# Single Notebook With All the Code to Go From List of Science Job Titles to geoJSON of Companies advertising those jobs on a map

------------------------------------------------

# General Outline
### get list of science related jobs
    * Clean up a list of science related job titles I modified from wikipedia in excel, save as csv
### get company names that are hiring for those science related job titles in Houston, TX by scraping job search site(s)
    * use beautiful soup, a python library to gather information from websites programtically and return list of companies
    * Clean up duplication and companies that shouldn't be included
### get addresses and lat longs associated with each company name in json form
    * use google places API to search for company name and a Houston, TX location, returning json of location and company information
    * clean returned list of json data such that it is limited to a lat long box of the greater houston area
    * clean up duplicates and are false positives useing pandas and other python libraries to 
### convert results to geoJSON. Add-in additional data dimensions, such as job title used in seach, as geoJSON properties
    * use geoJSON and JSON python libraries to convert previous json into points, and then features, and then a single feature collection
### get geoJSONs from other sources that contain science location data on things like schools and hospitals
    * use .... a http get call to access the geoJSON files already created by the city of Houston.
### add geoJSONs to map. Use color, size, and shape to represent different geoJSON properties. Tell a story
    * use mapboxGL.js, leaflet.js, and basic html/CSS/JS to create maps

### importing needed python modules

In [3]:
#### Imports for parts #1 & #2
from bs4 import BeautifulSoup # For HTML parsing
from urllib.request import urlopen
import re # Regular expressions
from time import sleep # To prevent overwhelming the server between connections
from collections import Counter # Keep track of our term counts
from nltk.corpus import stopwords # Filter out stopwords, such as 'the', 'or', 'and'
import pandas as pd # For converting results to a dataframe and bar chart plots
%matplotlib inline
import json
import csv

##### Import modules for google API and geoJSON parts. Only duplicate is json
import requests
import configparser
import json
import geojson
from geojson import Point, Feature, FeatureCollection
# https://github.com/frewsxcv/python-geojson
import time
import pandas as pd

===================================================================================

# 1. Load list of job titles

------------------------------------------------------------------------------

In [4]:
with open('../Data/science_jobs_v2.csv', 'rt') as f:
    reader = csv.reader(f)
    science_jobs_list_withInfo = list(reader)

job_title_list = []
for each in science_jobs_list_withInfo:
    each = each[0]
    #print('each',each)
    job_title_list.append(each)

# take out the header 'Job_Title'
job_title_list.pop(0)

print(job_title_list)

['Bioanalytical Scientist', 'Biochemist', 'Biochemistry', 'Bioinformatics Research Scientist', 'Biological Engineer', 'Biologist', 'biology  ', 'biomechanical', 'Biomedical scientist', 'biophysics', 'Cell Line', 'Clinical Data', 'Clinical Data Research', 'Clinical Pharmacology Professor', 'Clinical Pharmacy Assistant', 'Clinical Research Associate', 'Drug Evaluator', 'Drug Regulatory Affairs Manager', 'Environmental Health Scientist', 'Genetic Counselor', 'Health Research', 'Health Technology', 'Healthcare science', 'Hospital Research Assistant', 'Immunology Scientist', 'Life Science', 'Medical', 'Medical Center', 'medical Laboratory', 'Medical laboratory scientist', 'Medical Physics Researcher', 'Medical Research Assistant', 'Medical Research Technician', 'Medical Scientist', 'Microbiologist', 'Molecular Biologist', 'Molecular physics', 'Neuroscientist', 'Nuclear', 'Oncology Researcher', 'Pathologist', 'Pharmaceutical Assistant', 'Pharmaceutical Research Analyst', 'Pharmaceutical Rese

In [6]:
short_job_title_list_old1stHalf = ['Biochemistry', 'Bioinformatics', 'Biologist', 'biomechanical', 'Biomedical', 'biophysics', 'Cell+Line', 'Clinical+Data', 'Pharmacology', 'Pharmacy', 'Drug Evaluator', 'Environmental Health', 'Genetic Counselor', 'Healthcare', 'Hospital', 'Immunology', 'Life Science', 'Medical', 'Medical Center', 'medical Laboratory', 'Medical Physics', 'Medical', 'Microbiologist', 'Neuroscientist', 'Nuclear', 'Oncology', 'Pathologist', 'Pharmaceutical', 'Photochemistry', 'Public Health Specialist', 'radiobiology', 'Radiochemistry', 'Toxicologist', 'Agricultural', 'Archaeologist', 'Associate Professor', 'Botanist', 'botany', 'Chemical', 'Chemist', 'Conservation', 'Forensic Chemist', 'Herpetologist', 'Laboratory', 'meteorologist ', 'Naturalist', 'Oceanographer', 'oceanography', 'optomitrist']

In [93]:
short_job_title_list_1stHalf = ['Chemist', 'Conservation', 'Forensic Chemist', 'Herpetologist', 'Laboratory', 'meteorologist ', 'Naturalist', 'Oceanographer', 'oceanography', 'optomitrist']

In [91]:
len(short_job_title_list_old1stHalf)

49

In [86]:
short_job_title_list_2ndHalf = ['Forensic Scientist','Physical Scientist','Psychologist', 'Research Fellow', 'Science teacher', 'Scientist', 'social science', 'Solid-state', 'STEM', 'Stem Cell', 'Stereochemistry', 'Volcanologist', 'volcanology', 'wind power', 'wind turbine ', 'zoo', 'Zoologist', 'zoology ', 'chemistry', 'Crystallography', 'Earth Science', 'Ecologist', 'Ecology', 'Environmental', 'Exploration', 'fluid dynamics', 'geochemist', 'Geochemistry', 'Geographer', 'Geologist', 'geology ', 'geophysicist', 'GiS ', 'Groundwater Technician', 'hydrology', 'Inorganic', 'lab technician', 'Materials science', 'micropaleontologist', 'operations geologist', 'paleoclimatology', 'paleoecology', 'Paleontologist', 'Petroleum geologist', 'petrophysicist', 'playnology', 'reservoir', 'modeler', 'rock Laboratory', 'sedimentologist', 'stratigraphy', 'subsea', 'aeronautics', 'Aerospace', 'astrobiology', 'Astrochemistry', 'astromaterials', 'Astronaut', 'Astronomer', 'astronomy', 'astrophysics', 'Food chemistry', 'heliophysics', 'International Space Station', 'Johnson Space Center', 'lunar', 'materials', 'NASA', 'Physicist', 'physics', 'Planetary', 'propulsion engineer', 'Satellite', 'Space science', 'telemetry']

In [92]:
len(short_job_title_list_2ndHalf)

75

In [87]:
test_short_job_title_list = ['Chemist', 'Conservation', 'Herpetologist', 'Laboratory', 'meteorologist ', 'Naturalist']

In [88]:
len(short_job_title_list)

10

In [10]:
# replace some of the characters so the search is a bit better:
def cleanCompanies(company_array):
    new_array = []
    for each in company_array:
        #print(each, "and type is ",type(each))
        print(each.find("-",0))
        print(type(each.find("-",0)),"type of each.find('-',0")
        #print(type(each.find("%2C",1)))
        if each.find("%2C",1) is not -1:
            each = each.replace("%2C",",")
            print(each,"= each")
        else:
            each = each
        if each.find("%26",1) is not -1:
            each = each.replace("%26","&")
            #print(each,"= each find")
        else:
            each = each
        ##print(each, "again with each")
        if  each.find("-1",1) is not -1:
            each = each.replace("-1","")
        #    print(each,"= each find")
        else:
            each = each
        if  each.find("-2",0) is not -1:
            each = each.replace("-2","")
            print(each,"= each find")
        else: 
            each = each
        if  each.find("-3",0) is not -1:
            each = each.replace("-3","")
        #    print(each,"= each find")
        else:
            each
        if  each.find("-",1) is not -1:
            each = each.replace("-","+")
            print(each,"= each find")
        else:
            each = each
        if  each.find(" ",1) is not -1:
            each = each.replace(" ","+")
            print(each,"= each find")
        else:
            each = each
        print("each at end",each)
        new_array.extend([each])
    print('new_array',new_array)
    return new_array

In [11]:
short_job_title_list = cleanCompanies(short_job_title_list)
short_job_title_list

-1
<class 'int'> type of each.find('-',0
each at end Chemist
-1
<class 'int'> type of each.find('-',0
each at end Conservation
-1
<class 'int'> type of each.find('-',0
Forensic+Chemist = each find
each at end Forensic+Chemist
-1
<class 'int'> type of each.find('-',0
each at end Herpetologist
-1
<class 'int'> type of each.find('-',0
each at end Laboratory
-1
<class 'int'> type of each.find('-',0
meteorologist+ = each find
each at end meteorologist+
-1
<class 'int'> type of each.find('-',0
each at end Naturalist
-1
<class 'int'> type of each.find('-',0
each at end Oceanographer
-1
<class 'int'> type of each.find('-',0
each at end oceanography
-1
<class 'int'> type of each.find('-',0
each at end optomitrist
new_array ['Chemist', 'Conservation', 'Forensic+Chemist', 'Herpetologist', 'Laboratory', 'meteorologist+', 'Naturalist', 'Oceanographer', 'oceanography', 'optomitrist']


['Chemist',
 'Conservation',
 'Forensic+Chemist',
 'Herpetologist',
 'Laboratory',
 'meteorologist+',
 'Naturalist',
 'Oceanographer',
 'oceanography',
 'optomitrist']

In [12]:
len(short_job_title_list)

10

------------------------------------------------------------------------------
# 2. Get company names that are hiring for those science related job titles in Houston, TX by scraping job search site(s)
------------------------------------------------------------------------------


=========================================================================================
## A data exploration using beautiful soup
- based on this: https://jessesw.com/Data-Science-Skills/

### The function 'skills_info' takes three arguments; city, state, and job title and returns a list of companies searching for that job title in the last 30 days in Houston, TX

In [14]:
def skills_info(city="Houston", state="TX",job_title='data+scientist'):
    '''
    This function will take a desired city/state and look for all new job postings
    on Indeed.com. It will crawl all of the job postings and keep track of how many
    use a preset list of typical data science skills. The final percentage for each skill
    is then displayed at the end of the collation. 
        
    Inputs: The location's city and state. These are optional. If no city/state is input, 
    the function will assume a national search (this can take a while!!!).
    Input the city/state as strings, such as skills_info('Chicago', 'IL').
    Use a two letter abbreviation for the state.
    '''
    #print("test1")   
    final_job = job_title # searching for data scientist exact fit("data scientist" on Indeed search)
    
    # Make sure the city specified works properly if it has more than one word (such as San Francisco)  %22&l=
    if city is not None:
        final_city = city.split() 
        final_city = '+'.join(word for word in final_city)
        final_site_list = ['https://www.indeed.com/jobs?q=', final_job, '&l=', final_city,'%2C+', state] # Join all of our strings together so that indeed will search correctly
    else:
        final_site_list = ['https://www.indeed.com/jobs?q="', final_job, '"']

    final_site = ''.join(final_site_list) # Merge the html address together into one string

    # website query today (2017-02-25) is = https://www.indeed.com/jobs?q=data+scientist&l=Houston%2CTX
        
    base_url = 'http://www.indeed.com'
    
    #print("test2")  
    try:
        html = urlopen(final_site).read() # Open up the front page of our search first
    except:
        #print('That city/state combination did not have any jobs. Exiting . . .') # In case the city is invalid
        return
    soup = BeautifulSoup(html,"lxml") # Get the html from the first page
    
    # Now find out how many jobs there were
    
    if type(soup.find(id = 'searchCount')) is None or type(soup.find(id = 'searchCount')) == None:
        c
    
    else:
        variableS = soup.find(id = 'searchCount')
        if isinstance(variableS,type(None)):
            all_company_results = []
            return all_company_results
        else:
            print("soup.find(id = 'searchCount') = ",soup.find(id = 'searchCount'))
            print("soup.find(id = 'searchCount') = ",type(soup.find(id = 'searchCount')))

            num_jobs_area = soup.find(id = 'searchCount').string.encode('utf-8') # Now extract the total number of jobs found
                                                                                # The 'searchCount' object has this
            #print('num_jobs_area before filtering ', num_jobs_area)

            job_numbers = re.findall(b'\d+', num_jobs_area) # Extract the total jobs found from the search result

            #print('job number before filtering ', job_numbers[2])

            job_numbers_decoded = int(job_numbers[2].decode('utf-8'))
            #print('job_numbers_decoded = ',job_numbers_decoded, "type is ",type(job_numbers_decoded))

            #if len(job_numbers[2]) > 3: # Have a total number of jobs greater than 1000
            #    total_num_jobs = (int(job_numbers[2])*1000) + int(job_numbers[3])
            #else:
            #    total_num_jobs = int(job_numbers[2]) 

            total_num_jobs = job_numbers_decoded

            city_title = city
            if city is None:
                city_title = 'Nationwide'

            #print('There were', total_num_jobs, 'jobs found,', city_title) # Display how many jobs were found

            # took out /10 here, which seemed to be assuming always 10 results per page? now 15?
            num_pages = int(float(total_num_jobs/10)) # This will be how we know the number of times we need to iterate over each new
                                              # search result page

            job_descriptions = [] # Store all our descriptions in this list

            # used to be 'xrange' here but I changed it to 'range' because I'm using python3 and xrange is python2 only
            all_company_results = []
            for i in range(1,num_pages+1): # Loop through all of our search result pages
                #print('Getting page', i)

                start_num = str(i*10) # Assign the multiplier of 10 to view the pages we want
                current_page = ''.join([final_site, '&start=', start_num])
                # Now that we can view the correct 10 job returns, start collecting the text samples from each

                html_page = urlopen(current_page).read() # Get the page

                page_obj = BeautifulSoup(html_page,"lxml") # Locate all of the job links
                job_link_area = page_obj.find(id = 'resultsCol') # The center column on the page where the job postings exist
                #print('page_obj',page_obj)  

                #print("link.get('href')",base_url + link.get('href')
                #print("job_link_area.find_all('a')",job_link_area.find_all('a'))

                for a in job_link_area.find_all('a', href=True):
                    #print ("Found the URL:", a['href'])
                    if "/cmp/" in a['href']: 
                        #  if a['href'].find("/cmp/"):
                        #print("a had /cmp/ in it using find = ",a['href'])
                        arrayHrefParts_0 = a['href'].split('/cmp/')
                        #print("aarrayHrefParts_0 = ",arrayHrefParts_0)
                        arrayHrefParts_1 = arrayHrefParts_0[1].split('/')
                        #print("arrayHrefParts_1 = ",arrayHrefParts_1)
                        company = arrayHrefParts_1[0]
                        #print('company = ',company)
                        all_company_results.append(company)
                        #print('all_company_results =',all_company_results)
                    else:
                        continue
                        #print("/cmp/ not found in ,",a['href'])

                #print("[base_url + link.get('href') for link in job_link_area.find_all('a')]",[base_url + link.get('href') for link in job_link_area.find_all('a')])

                #job_URLS = [base_url + link.get('href') for link in job_link_area.find_all('a')] # Get the URLS for the jobs

                #job_URLS = filter(lambda x:'clk' in x, job_URLS) # Now get just the job related URLS


                #         for j in xrange(0,len(job_URLS)):
                #             final_description = text_cleaner(job_URLS[j])
                #             if final_description: # So that we only append when the website was accessed correctly
                #                 job_descriptions.append(final_description)
                #             sleep(1) # So that we don't be jerks. If you have a very fast internet connection you could hit the server a lot! 

                sleep(1) # So that we don't be jerks. If you have a very fast internet connection you could hit the server a lot! 

            for each in range(len(all_company_results)):
                if '.html' in all_company_results[each]:
                    #print('all_company_results[each]',all_company_results[each]," each = ",each)
                    new_name_wo_html = all_company_results[each].split('.html')[0]
                    #print('new_name_wo_html',new_name_wo_html)
                    all_company_results[each] = new_name_wo_html  

            all_company_results = list(set(all_company_results))
            #print ('Done with collecting the job postings!')    
            #print ('all_company_results final = ',all_company_results)
            #print ("There were",len(all_company_results)," companies successfully found.")
            all_company_results_json = []
            for each in all_company_results:
                print("each in all_company_results = ",each)
                print("job_title in all_company_results = ",job_title)
                temp_obj_holder = {"company":"nothing","job_title":"nothing"}
                print("temp_obj_holder = ",temp_obj_holder)
                temp_obj_holder["job_title"] = job_title
                temp_obj_holder["company"] = each
                print("temp_obj_holder['job_title'] = ",temp_obj_holder["job_title"])
                all_company_results_json.append(temp_obj_holder)
            return all_company_results_json


### The function 'runMultiple_skills_info' runs the 'skills_info' function multiple times, one for each job title in the list given to 'runMultiple_skills_info' function

In [15]:
def runMultiple_skills_info(array_of_jobTitles=['puppies']):
    all_results = []
    for each in array_of_jobTitles:
        print('each= ',each)
        #temp_results1 = []
        temp_results1 = skills_info("Houston","TX",each)
        if temp_results1 is None:
            continue
        else:
            print('temp_results is ',temp_results1)
            #all_results.extend(temp_results1) 
            all_results.extend(temp_results1)
    return all_results

###  | run a first test, should get back an array of objects with keys of company and job_title

In [16]:
array2 = ['geologist','geophysicist']


### create a small array for testing purposes

In [78]:
geo_and_geo = runMultiple_skills_info(array_of_jobTitles=array2)

each=  geologist
soup.find(id = 'searchCount') =  <div id="searchCount">Jobs 1 to 10 of 44</div>
soup.find(id = 'searchCount') =  <class 'bs4.element.Tag'>
each in all_company_results =  Rbc
job_title in all_company_results =  geologist
temp_obj_holder =  {'company': 'nothing', 'job_title': 'nothing'}
temp_obj_holder['job_title'] =  geologist
each in all_company_results =  Hess-Corporation
job_title in all_company_results =  geologist
temp_obj_holder =  {'company': 'nothing', 'job_title': 'nothing'}
temp_obj_holder['job_title'] =  geologist
each in all_company_results =  Tolunay--wong-Engineers,-Inc.
job_title in all_company_results =  geologist
temp_obj_holder =  {'company': 'nothing', 'job_title': 'nothing'}
temp_obj_holder['job_title'] =  geologist
each in all_company_results =  Bhp-Billiton
job_title in all_company_results =  geologist
temp_obj_holder =  {'company': 'nothing', 'job_title': 'nothing'}
temp_obj_holder['job_title'] =  geologist
each in all_company_results =  Enrud-Res

In [79]:
geo_and_geo

[{'company': 'Rbc', 'job_title': 'geologist'},
 {'company': 'Hess-Corporation', 'job_title': 'geologist'},
 {'company': 'Tolunay--wong-Engineers,-Inc.', 'job_title': 'geologist'},
 {'company': 'Bhp-Billiton', 'job_title': 'geologist'},
 {'company': 'Enrud-Resources', 'job_title': 'geologist'},
 {'company': 'W&T-Offshore,-Inc.', 'job_title': 'geologist'},
 {'company': 'SAN-Jacinto-College', 'job_title': 'geologist'},
 {'company': 'Bmo-Financial-Group', 'job_title': 'geologist'},
 {'company': 'Jefferies', 'job_title': 'geologist'},
 {'company': 'Fugro', 'job_title': 'geologist'},
 {'company': 'Walker-Elliott', 'job_title': 'geologist'},
 {'company': 'Hilcorp-Energy-Company', 'job_title': 'geologist'},
 {'company': 'Occidental-Petroleum', 'job_title': 'geologist'},
 {'company': 'Murray-Resources', 'job_title': 'geologist'},
 {'company': 'Intera', 'job_title': 'geologist'},
 {'company': 'High-Country-Executive-Search', 'job_title': 'geologist'},
 {'company': 'Weatherford', 'job_title': 'ge

In [19]:
def saveArray_of_JobSearchResults(arrayOfJobsAndSearchTerm, FilePath):
    toCSV = arrayOfJobsAndSearchTerm
    keys = toCSV[0].keys()
    with open(FilePath, 'w') as output_file:
        dict_writer = csv.DictWriter(output_file, keys)
        dict_writer.writeheader()
        dict_writer.writerows(toCSV)
    return arrayOfJobsAndSearchTerm
    

In [91]:
saveArray_of_JobSearchResults(arrayOfJobsAndSearchTerm = geo_and_geo, FilePath ='../DATA/test_jobSearchTermAndCompany_geoAndgeo_v4.csv')

####  | end test

#### Review:

3 functions:
- A. skills_info(city="Houston", state="TX",job_title='data+scientist')
- B. runMultiple_skills_info(array_of_jobTitles=['puppies'])
- C. saveArray_of_JobSearchResults(arrayOfJobsAndSearchTerm = geo_and_geo, FilePath ='../DATA/someFile')

A does the web scraping. B does web scraping searching for each of the items in the input array and combines the resuls. C saves the results as a csv file with two columns. One column header is Job Title used in search. The other column is company name looking for that job title in Houston Texas. 

------------------------------------------------------------------------------
# 3. Get addresses and lat longs associated with each company name in json form
------------------------------------------------------------------------------


### Modules imported at top of this notebook

### using <a href="https://docs.python.org/3/library/configparser.html">configparser</a> to handle config file 

In [20]:
config = configparser.ConfigParser()

In [21]:
configFilePath = '../config.conf'
# configparser.ConfigParser().read(configFilePath)
config.read(configFilePath)

['../config.conf']

### next block sets a variety of useful variables used in the google places API

In [22]:
#### sets key as variable that contains the google-places-api key
key = config['google-places-api']['key1']
#### creates a string used as the prefix to the key in the url used in calling the API service
key_pre = '&key='
#### the base url in the google places API get call
base_url = 'https://maps.googleapis.com/maps/api/place/textsearch/json?query='
#### the base url when calling a next page, in other words, when results are more than 20
next_page_base_url = 'https://maps.googleapis.com/maps/api/place/textsearch/json?'

### load into memory the csv previously created with the company names and job titles that go with them

In [92]:
# using pandas as pd. Pandas should already be imported
df=pd.read_csv('../DATA/test_jobSearchTermAndCompany_geoAndgeo_v4.csv', sep=',',header=None)
company_array = df.values

len(company_array)

40

In [93]:
company_array

array([['company', 'job_title'],
       ['Rbc', 'geologist'],
       ['Hess-Corporation', 'geologist'],
       ['Tolunay--wong-Engineers,-Inc.', 'geologist'],
       ['Bhp-Billiton', 'geologist'],
       ['Enrud-Resources', 'geologist'],
       ['W&T-Offshore,-Inc.', 'geologist'],
       ['SAN-Jacinto-College', 'geologist'],
       ['Bmo-Financial-Group', 'geologist'],
       ['Jefferies', 'geologist'],
       ['Fugro', 'geologist'],
       ['Walker-Elliott', 'geologist'],
       ['Hilcorp-Energy-Company', 'geologist'],
       ['Occidental-Petroleum', 'geologist'],
       ['Murray-Resources', 'geologist'],
       ['Intera', 'geologist'],
       ['High-Country-Executive-Search', 'geologist'],
       ['Weatherford', 'geologist'],
       ['University-of-Houston--downtown', 'geologist'],
       ['Jefferies-&-Company,-Inc.', 'geologist'],
       ['Oasis-Petroleum', 'geologist'],
       ['Hart-Energy', 'geologist'],
       ['Sinopec-Tech-Houston', 'geologist'],
       ['Citi', 'geologist'],


In [40]:
# replace some of the characters so the search is a bit better:
def cleanCompanies(company_array):
    company_array = company_array[1:]
    new_array = []
    for each in company_array:
        job_title = each[1]
        each = each[0]
        #print(each, "and type is ",type(each))
        print(each.find("-",0))
        print(type(each.find("-",0)),"type of each.find('-',0")
        #print(type(each.find("%2C",1)))
        if each.find("%2C",1) is not -1:
            each = each.replace("%2C",",")
            print(each,"= each")
        else:
            each = each
        if each.find("%26",1) is not -1:
            each = each.replace("%26","&")
            #print(each,"= each find")
        else:
            each = each
        ##print(each, "again with each")
        if  each.find("-1",1) is not -1:
            each = each.replace("-1","")
        #    print(each,"= each find")
        else:
            each = each
        if  each.find("-2",0) is not -1:
            each = each.replace("-2","")
            print(each,"= each find")
        else: 
            each = each
        if  each.find("-3",0) is not -1:
            each = each.replace("-3","")
        #    print(each,"= each find")
        else:
            each = each
        if  each.find("-",1) is not -1:
            each = each.replace("-","+")
            print(each,"= each find")
        else:
            each = each
        print("each at end",each)
        new_array.extend([[each,job_title]])
    print('new_array',new_array)
    return new_array

In [151]:
company_array_formatted = cleanCompanies(company_array)
company_array_formatted

-1
<class 'int'> type of each.find('-',0
each at end Rbc
4
<class 'int'> type of each.find('-',0
Hess+Corporation = each find
each at end Hess+Corporation
7
<class 'int'> type of each.find('-',0
Tolunay++wong+Engineers,+Inc. = each find
each at end Tolunay++wong+Engineers,+Inc.
3
<class 'int'> type of each.find('-',0
Bhp+Billiton = each find
each at end Bhp+Billiton
5
<class 'int'> type of each.find('-',0
Enrud+Resources = each find
each at end Enrud+Resources
3
<class 'int'> type of each.find('-',0
W&T+Offshore,+Inc. = each find
each at end W&T+Offshore,+Inc.
3
<class 'int'> type of each.find('-',0
SAN+Jacinto+College = each find
each at end SAN+Jacinto+College
3
<class 'int'> type of each.find('-',0
Bmo+Financial+Group = each find
each at end Bmo+Financial+Group
-1
<class 'int'> type of each.find('-',0
each at end Jefferies
-1
<class 'int'> type of each.find('-',0
each at end Fugro
6
<class 'int'> type of each.find('-',0
Walker+Elliott = each find
each at end Walker+Elliott
7
<class 

[['Rbc', 'geologist'],
 ['Hess+Corporation', 'geologist'],
 ['Tolunay++wong+Engineers,+Inc.', 'geologist'],
 ['Bhp+Billiton', 'geologist'],
 ['Enrud+Resources', 'geologist'],
 ['W&T+Offshore,+Inc.', 'geologist'],
 ['SAN+Jacinto+College', 'geologist'],
 ['Bmo+Financial+Group', 'geologist'],
 ['Jefferies', 'geologist'],
 ['Fugro', 'geologist'],
 ['Walker+Elliott', 'geologist'],
 ['Hilcorp+Energy+Company', 'geologist'],
 ['Occidental+Petroleum', 'geologist'],
 ['Murray+Resources', 'geologist'],
 ['Intera', 'geologist'],
 ['High+Country+Executive+Search', 'geologist'],
 ['Weatherford', 'geologist'],
 ['University+of+Houston++downtown', 'geologist'],
 ['Jefferies+&+Company,+Inc.', 'geologist'],
 ['Oasis+Petroleum', 'geologist'],
 ['Hart+Energy', 'geologist'],
 ['Sinopec+Tech+Houston', 'geologist'],
 ['Citi', 'geologist'],
 ['Confidential+++Oil+&+Gas+Company', 'geologist'],
 ['Marathon+Oil', 'geologist'],
 ['New+Tech+Global', 'geologist'],
 ['Lonestar+College+System', 'geologist'],
 ['Geotra

### All the functions that load and clean the company + job title list from csv into memory

In [45]:
def load_listCompanyJobtitle(path):
    df=pd.read_csv(path,header=None)
    company_array = df.values
    company_array_formatted = cleanCompanies(company_array)
    return company_array_formatted

### Next few functions run the company names through the google places API

##### Below is the main function that calls the Google Places API to get the initial results

In [25]:
# function that takes a datset that is 
def callGooglePlacesAPI(search_term,nameOfSearch,job_title):
    print('job_title put into googleAPI call is =',job_title)
    dataset_I = requests.get(base_url+search_term+key_pre+key)
    next_page_result = []
    try:
        next_page_token = dataset_I.json()['next_page_token']
        next_page_result = callNextPageResults(nameOfSearch,next_page_token,job_title)
    except: 
        pass
    #####if 'next_page_token' in dataset_I:
    #next_page_token = dataset_I.json()['next_page_token']
    #print("next_page_token",next_page_token)
    #callNextPageResults(nameOfSearch,next_page_token)
    #####next_page_results = makeFeatureCollectionsFromPlaces(dataset_I['next_page_token'],nameOfSearch).json()['results']
    ##### #else: 
    ####    next_page = "none needed"
    dataset = dataset_I.json()['results']
    #if 'next_page_token' in dataset_I:
    #    dataset.extend(next_page_results)
    #    print("dataset up top",dataset)
    #else:
    #    next_page = "none needed"
    array_of_features = []
    for each in dataset:
        photos = []
        # centerpoint for coordinates
        #print(each)
        lat = each['geometry']['location']['lat']
        long = each['geometry']['location']['lng']
        # properties
        address = each['formatted_address']
        id = each['id']
        name = each['name']
        # photos is an array
        try:
            photos = each['photos']
        except:
            photos = []
            #print("photos , attribute error but kept going")
        place_id = each['place_id']
        try:
            rating = each['rating']
        except:
            rating = 'NA'
            #print("rating , attribute error but kept going")
        reference = each['reference']
        # types is an array
        types = each['types']
        testPoint = Point((long, lat))
        test2_geoJSOn = Feature(geometry=testPoint, properties={"job_title":job_title,"name": name,"address":address,"id":id,"photos":photos,"place_id":place_id,"rating":rating,"reference":reference,"types":types})
        array_of_features.extend([test2_geoJSOn])
#     new_FeatureCollection = FeatureCollection(array_of_features) 
#     with open('../DATA/'+nameOfSearch+'_test.geojson', 'w') as f:
#         json.dump(new_FeatureCollection, f)
#     return new_FeatureCollection
    print("array_of_features = ",array_of_features," and next_page_result = ",next_page_result)
    print("types: for "+search_term+" type(next_page_result)= ",type(next_page_result)," and type(array_of_features)=  ",type(array_of_features))
    if next_page_result is None or next_page_result==[]:
        fakeVariable = 3
        #print("no second page")
    else:
        #print("next_page_result passed none test and is ",next_page_result)
        array_of_features.extend(next_page_result)
        #print("array_of_features after extension = ",array_of_features)
    #print("2nd statement of array_of_features = ",array_of_features)
    return array_of_features

##### Below is a secondary function that calls the Google Places API "next page" to get any results further additional to the first 40. 

In [26]:
def callNextPageResults(nameOfSearch,keyForNextPage,job_title):
    time.sleep(5)
    #print('next_page_base_url+"&pagetoken="+keyForNextPage+key_pre+key =',next_page_base_url+"pagetoken="+keyForNextPage+key_pre+key)
    dataset_I = requests.get(next_page_base_url+"pagetoken="+keyForNextPage+key_pre+key)
    #print("dataset_I second page full response",dataset_I.json())
    dataset = dataset_I.json()['results']
    array_of_features = []
    for each in dataset:
        photos = []
        # centerpoint for coordinates
        #print(each)
        lat = each['geometry']['location']['lat']
        long = each['geometry']['location']['lng']
        # properties
        address = each['formatted_address']
        id = each['id']
        name = each['name']
        # photos is an array
        try:
            photos = each['photos']
        except:
            photos = []
            #print("photos , attribute error but kept going")
        place_id = each['place_id']
        try:
            rating = each['rating']
        except:
            rating = 'NA'
            #print("rating , attribute error but kept going")
        reference = each['reference']
        # types is an array
        types = each['types']
        testPoint = Point((long, lat))
        test2_geoJSOn = Feature(geometry=testPoint, properties={"job_title":job_title,"name": name,"address":address,"id":id,"photos":photos,"place_id":place_id,"rating":rating,"reference":reference,"types":types})
        array_of_features.extend([test2_geoJSOn])
    #new_FeatureCollection = FeatureCollection(array_of_features) 
    #with open('../DATA/'+nameOfSearch+'_2ndPage_test.geojson', 'w') as f:
    #    json.dump(new_FeatureCollection, f)
    #print("second page results = ",new_FeatureCollection)
    #return new_FeatureCollection
    return array_of_features

##### Below is the a function that runs through a list and calls the two functions above and combines the results into a single result

In [81]:
def create_List_Features(cp_array_formatted):
    array_of_all_features = []
    print("in function create_List_Features, cp_array_formatted[0][0]",cp_array_formatted[0][0])
    for each in cp_array_formatted:
        #try:
        features_1 = callGooglePlacesAPI(each[1]+"+Houston+Texas","random_for_now",each[0])
        #print("features for a company name =",features_1)
        if array_of_all_features == [] or array_of_all_features is None:
            array_of_all_features = features_1
        else:
            if features_1 is None or features_1 == []:
                pass
            else:
                array_of_all_features.extend(features_1)
        #except:
        #    print("error in except",error)
        
        #print("array_of_all_features = ",array_of_all_features)
    
    return array_of_all_features

##### function that takes a list of features and returns a feature collection

In [73]:
# creates feature collection from list of features
def createFeatureCollection(list_of_features,geographic_limits):
    slimmed_featList = []
    print('geographic_limits =',geographic_limits)
    for each in list_of_features:
        print("each = ",each)
        print("each['geometry']['coordinates']",each['geometry']['coordinates'])
        print("each['geometry']['coordinates'][0] =",each['geometry']['coordinates'][0])
        if each['geometry']['coordinates'][0] > geographic_limits["west_limit"] and each['geometry']['coordinates'][0] < geographic_limits["east_limit"] and each['geometry']['coordinates'][1] < geographic_limits["north_limit"] and each['geometry']['coordinates'][1] > geographic_limits["south_limit"]:
            slimmed_featList.append(each)
    
    
    print('finished the function createFeatureCollection and slimmed featureList is slimmed_featList',slimmed_featList)
    return FeatureCollection(slimmed_featList)



##### function that takes the return from the above function and saves it as a geoJSON file

 30°15'6.44"N   96° 5'17.13"W
  29°16'56.13"N  95°57'46.47"W
   29°21'28.30"N   94°38'24.37"W
    30°26'55.88"N   94°48'6.63"W
    
    north limit = 30°26'55.88      30.44885556
    south limit = 29°16'56.13"N     29.28225833
    west limit = 96° 5'17.13"W     -96.08805556
    east limit = 94°38'24.37"W     -94.64000000
   

In [74]:
# convert feature collection to geoJSON
def convertFeatureCollectionToGeoJSON(featCollection,fileNamePath):
    print('got to the function convertFeatureCollectionToGeoJSON')
    with open(fileNamePath, 'w') as f:
        json.dump(featCollection, f)



#### function that calls the others. It takes as arguments the list of companies and job_titles & the path to save the resulting geojson to

In [75]:
def make_geojson_from_CompanyJobList(company_list_formatted,path,geographic_limits):
    #### function that calls the google api and returns results in terms of a list of feature
    print("make_geojson_from_CompanyJobList(company_list_formatted = ",company_list_formatted)
    list_of_features = create_List_Features(company_list_formatted)
    #### function that creates a feature collection from the list of features
    featCollection = createFeatureCollection(list_of_features,geographic_limits)
    #### function that takes the feature collection and file path and saves the feature collection as a geoJSON file
    convertFeatureCollectionToGeoJSON(featCollection,path)
    return featCollection
    

### The geographic limits that trim down the results to only things around Houston as some jobs are advertised in Houston that aren't located in Houston

In [76]:
geographic_limits = {"north_limit":30.454961,"south_limit":28.956857,"west_limit":-96.206159,"east_limit":-94.64000000}

------------------------------------------------------------------------------
## Run Everything As Single Function
------------------------------------------------------------------------------

In [77]:
##def getJSON_from_jobsList_everything(array_of_job_Titles,FilePath,path=,geographic_limits = geographic_limits):
    #### returns list of companies advertising each job in an array of job titles
  ##  list_of_CompaniesAndJobs = runMultiple_skills_info(array_of_job_Titles)
    #### saves the list of lists from above... and formats it a bit further in prep for next step
 ##   Array_of_JobCompany_edA = saveArray_of_JobSearchResults(arrayOfJobsAndSearchTerm = list_of_CompaniesAndJobs, FilePath)
    print("in geoJSON_from_jobsList_everything, Array_of_JobCompany is =",Array_of_JobCompany)
    ##### opens and cleans the list of companies 
 ##   Array_of_JobCompany = load_listCompanyJobtitle(FilePath)
    #### runs the companies through the google places API
    #### combines the results into an array of features
    #### turns that into a feature collection 
    #### then saves as geojson
  ##  make_geojson_from_CompanyJobList(company_list_formatted = Array_of_JobCompany,path,geographic_limits = geographic_limits)



IndentationError: unexpected indent (<ipython-input-77-70e7b0b2da42>, line 6)

In [78]:
def getJSON_from_jobsList_everything(array_of_job_Titles,FilePath,path,geographic_limits):
    #### returns list of companies advertising each job in an array of job titles
    list_of_CompaniesAndJobs = runMultiple_skills_info(array_of_job_Titles)
    #### saves the list of lists from above... and formats it a bit further in prep for next step
    Array_of_JobCompany_edA = saveArray_of_JobSearchResults(list_of_CompaniesAndJobs, FilePath)
    print("in geoJSON_from_jobsList_everything, Array_of_JobCompany is =",Array_of_JobCompany_edA)
    ##### opens and cleans the list of companies 
    Array_of_JobCompany_cln = load_listCompanyJobtitle(FilePath)
    #### runs the companies through the google places API
    #### combines the results into an array of features
    #### turns that into a feature collection 
    #### then saves as geojson
    feature_collection = make_geojson_from_CompanyJobList(Array_of_JobCompany_cln,path,geographic_limits)
    #### returns the previously created feature collection for testing of result without reloading from geojson
    return feature_collection



Input_List_JobTitles = test_short_job_title_list

FilePath = '../DATA/test_jobSearchTermAndCompany_all_v3.csv'

path="../DATA/test_geojson_Everything_v3.geojson"

geographic_limits ={"north_limit":30.454961,"south_limit":28.956857,"west_limit":-96.206159,"east_limit":-94.64000000}

In [83]:
funcArg = {"ListJobTitles":test_short_job_title_list,"pCSV":'../DATA/test_jobTitleCompany_all_v5.csv',"pGeoJSON":"../DATA/test_geojson_Everything_v5.geojson","geo_lim":{"north_limit":30.454961,"south_limit":28.956857,"west_limit":-96.206159,"east_limit":-94.64000000}}

In [84]:
answer3  = getJSON_from_jobsList_everything(funcArg["ListJobTitles"],funcArg["pCSV"],funcArg["pGeoJSON"],funcArg["geo_lim"])

each=  Chemist
soup.find(id = 'searchCount') =  <div id="searchCount">Jobs 1 to 10 of 119</div>
soup.find(id = 'searchCount') =  <class 'bs4.element.Tag'>
each in all_company_results =  Texas-Children%27s-Hospital
job_title in all_company_results =  Chemist
temp_obj_holder =  {'job_title': 'nothing', 'company': 'nothing'}
temp_obj_holder['job_title'] =  Chemist
each in all_company_results =  Chamberlain-College-of-Nursing
job_title in all_company_results =  Chemist
temp_obj_holder =  {'job_title': 'nothing', 'company': 'nothing'}
temp_obj_holder['job_title'] =  Chemist
each in all_company_results =  O%27rourke-Petroleum
job_title in all_company_results =  Chemist
temp_obj_holder =  {'job_title': 'nothing', 'company': 'nothing'}
temp_obj_holder['job_title'] =  Chemist
each in all_company_results =  Lee-College
job_title in all_company_results =  Chemist
temp_obj_holder =  {'job_title': 'nothing', 'company': 'nothing'}
temp_obj_holder['job_title'] =  Chemist
each in all_company_results =

In [55]:
print(answer3)

None


In [82]:
test_asdfasdf = [{"geometry": {"coordinates": [-95.57188149999999, 29.9951915], "type": "Point"}, "properties": {"photos": [{"width": 4785, "height": 3190, "html_attributions": ["<a href=\"https://maps.google.com/maps/contrib/101403699241874436061/photos\">Chemistry</a>"], "photo_reference": "CoQBdwAAABqE-T9AB_70H655NJEo-6sBHiarzn_lCDTymGEOBYaQ_VCbs5x8DzItIaMFqpvhFvBUbKLnyMCbdmHoRSB8Gw9SBv-xixYqs_PO1MkakCQc5G4EUbL2I_OZhF1j1OMRPWWLbJ5LcaqG2gVCFBarTCL5nJlI3x9IBZuWr1GRdY63EhAhLTvv60bmRdTetY-GA-5bGhTqi4LVVI_9NX9ukVkXZFthqRiI7g"}], "types": ["beauty_salon", "spa", "health", "clothing_store", "store", "point_of_interest", "establishment"], "reference": "CmRSAAAA7c31MuvbVcIUj2yMiz3WauDMTcw7XdnZdlkrogYIlj0S6fqboTlV5cQpKrKyUielNqkPulDnLu7EAFsz6K1TBgaOdWI1qldreDqAywxQQY3lN9t_vThzZalbCwy1h1GYEhAaQ6uH_SB5CCv7izzBn12_GhTxqvH_YhNeFsTfq1YRorcaE4vCUg", "name": "Chemistry", "rating": 5, "id": "979d392b613c49fbb954ee393bff65bda5042b34", "job_title": "Texas-Children%27s-Hospital", "place_id": "ChIJWxsq_4fSQIYRU9dRPmk8uIw", "address": "126 Vintage Park Blvd N, Houston, TX 77070, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.34630229999999, 29.72187359999999], "type": "Point"}, "properties": {"photos": [{"width": 4160, "height": 3120, "html_attributions": ["<a href=\"https://maps.google.com/maps/contrib/108375995272754268174/photos\">Nitish Thareja</a>"], "photo_reference": "CoQBdwAAAEm8jBztuq9M8rJ6k2Tcq3_pcKXHaqkhmyQ51veW-2JgaVcKUJB3d--vFDl9rWkaQLV_EzACuyTS9jgzcdfww1_jIQ1WXM9b6f4TzXGq8Hm05xaDpBfKAp7ttWwPe2SHXssyS4R6E1AIklCofx8TmFIp5pjqn7mLttwhmKE8CznPEhCrkNH-pleFiZibwu5hHTZ4GhRi4C0Onj5HyMOHH2TBdHoJRJie7Q"}], "types": ["point_of_interest", "establishment"], "reference": "CmRSAAAAnq-Oh_KBA473bXhwtJpWW7jiAiSPx-efuMIBQzZ88ocupzw84U79MhRaHDpIsah6kMlhe3uY-hQC8XlR2RXQkpbDKgMaSkeaLkhUKOkYrb_HDW-FbTo-4ZqQKzbRA2_SEhBchQHeTDsV9gqbvdwfp-fnGhSLrHzShyYPnoxv3JIty2fd17hUtQ", "name": "University of Houston Department of Chemistry", "rating": 5, "id": "baa83832f81135d0180e7850ce768a11f32e9df5", "job_title": "Texas-Children%27s-Hospital", "place_id": "ChIJgRkjS1G-QIYRmcpaGaD6ZeY", "address": "3585 Cullen Blvd #112, Houston, TX 77004, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.4025992, 29.7198268], "type": "Point"}, "properties": {"photos": [], "types": ["point_of_interest", "establishment"], "reference": "CmRSAAAAorGMfnHRAdNBfkVQD3gWE1iKv9QdoaQz_IoZyjIII7V6LXRe3e5ZVW1Tca6It8hCPAUv0ph14CP6fig5TJGf-YLSGSltIdWFUJxn_MfAGVhjYwSTpizZ6-BQRAe1VxAsEhB5z8GcBdAhhORcmjGByQSbGhSONBQR81mEY2tCpIXMKlPYSf7D8w", "name": "Rice University - Department of Chemistry", "rating": 3, "id": "1553681e69a2414f5cfa7551caa2102bc22268c1", "job_title": "Texas-Children%27s-Hospital", "place_id": "ChIJL8yCnHzAQIYRZRcdAPRzhYI", "address": "6100 S Main St, Houston, TX 77005, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.4166517, 29.672442], "type": "Point"}, "properties": {"photos": [], "types": ["point_of_interest", "establishment"], "reference": "CmRSAAAAP3Jk3cwC1RKpWStjVrcIv_6mqQ2QKhvghOEPpeIGZ2hgexZxWXic00weFIhQmytv7xs0aerKIwMaExUCZUSR-f-WGR7JGLSlw33odAFDosENEYO62NTxykpSUF0rauMYEhBA7zbNGCGs1CQjACMddzM_GhQiWHTry-HleTDCNBg2rLzZ8CmiIQ", "name": "Environmental Chemistry Inc", "rating": "NA", "id": "940f1e5d70276d8a5feaa5242d817666afa7f4b2", "job_title": "Texas-Children%27s-Hospital", "place_id": "ChIJ7UpnzJjqQIYR2qG-Hcvp_YU", "address": "2525 W Bellfort St Ste 175, Houston, TX 77054, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.57188149999999, 29.9951915], "type": "Point"}, "properties": {"photos": [{"width": 4785, "height": 3190, "html_attributions": ["<a href=\"https://maps.google.com/maps/contrib/101403699241874436061/photos\">Chemistry</a>"], "photo_reference": "CoQBdwAAANRlVBSrPEw28u5HgwMsr5SB2Z4EZe__zXprH7mo6VPI2OzNc2meM7ULMwIVGFNN6pkwSH_PbxHmHp8y5j5-SWy9_sC_tb5322OtJzqZ0g4_mhFgi082SniQznSxR635Gd8TjmI2Odku-08eAwRZpoKdzhmLEHphnbF4PPKR4iwNEhAn7OxlVM2b7qbfIjeB_6X5GhRD2tl9noHI0V4jK_Rsp__Zj3KT6A"}], "types": ["beauty_salon", "spa", "health", "clothing_store", "store", "point_of_interest", "establishment"], "reference": "CmRSAAAA96Ejkv4uEUu17gGPdFIUTqNLqxI7T0E3S2YL5c4EU6l-o7TD8LTptPnwDqGLYF168rnfQl46l5I6n1XHqUluUWC8hOh_aBzlaSI2E5yUbo48EFLHg7rju9q8oXoc0YGbEhCHCmDB1jqRGrL7Z-P5wCt6GhS5FQHhwGA67doTuRgxCcfLOB5PmQ", "name": "Chemistry", "rating": 5, "id": "979d392b613c49fbb954ee393bff65bda5042b34", "job_title": "Ut-Health-Science-Center-At-Houston", "place_id": "ChIJWxsq_4fSQIYRU9dRPmk8uIw", "address": "126 Vintage Park Blvd N, Houston, TX 77070, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.34630229999999, 29.72187359999999], "type": "Point"}, "properties": {"photos": [{"width": 4160, "height": 3120, "html_attributions": ["<a href=\"https://maps.google.com/maps/contrib/108375995272754268174/photos\">Nitish Thareja</a>"], "photo_reference": "CoQBdwAAAGTMr8ZAuOdD8kLPiwKIkNxTaQqdjzvnciBs9qpb2-qDTXgTklEkxBMitzQuFCihGZraYFLW4fxEmD8RR_DcY-jTxo8HhSY4KfrEKSs0jMG2OOKc4On1vCDYhrew9F9ZxEqlOq0tROZN11AtC4bICqAJH5469VVHu7-t1r-uEoQaEhCcnhVGMgSKXuwIcCWoUKZXGhTlbZoiUJuk_tKgAbtLpHVY7jVE6Q"}], "types": ["point_of_interest", "establishment"], "reference": "CmRSAAAA5pIGg3l4Tu91ZV0g6SWJdjVxz0SgD6_nsfVmccKTdp0cxO442B6f6c_NRFdwqQ0FgD_4frB3UgDsyIoY8qMv_uLVwi83t7GCyIpyqGaxrqdhoXScG4zrqtQJjSbEz-LrEhCQc5kK8AsvpSWh3fZecKWqGhTBWyrvOiZR1AwfU-J-LYoZy7O6rg", "name": "University of Houston Department of Chemistry", "rating": 5, "id": "baa83832f81135d0180e7850ce768a11f32e9df5", "job_title": "Ut-Health-Science-Center-At-Houston", "place_id": "ChIJgRkjS1G-QIYRmcpaGaD6ZeY", "address": "3585 Cullen Blvd #112, Houston, TX 77004, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.4025992, 29.7198268], "type": "Point"}, "properties": {"photos": [], "types": ["point_of_interest", "establishment"], "reference": "CmRSAAAAZAreXmcbB0hzNCN0uUZ_bDoqJgvnchckqZG7qS-L4RfHGYBfduarcsqTDJT09KF_LyLIJ4BFVmIS5uE5gcDnpMbvW3VSTU2PNewp2ReLwzLrzf2CngZNszg3uVyheJR6EhDtu0T-WpJlacqErwyDBTm9GhRjYPl3DbhhjFa3eoJBT3LxoMEidw", "name": "Rice University - Department of Chemistry", "rating": 3, "id": "1553681e69a2414f5cfa7551caa2102bc22268c1", "job_title": "Ut-Health-Science-Center-At-Houston", "place_id": "ChIJL8yCnHzAQIYRZRcdAPRzhYI", "address": "6100 S Main St, Houston, TX 77005, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.4166517, 29.672442], "type": "Point"}, "properties": {"photos": [], "types": ["point_of_interest", "establishment"], "reference": "CmRSAAAAyMHiK8nb1mhCiDcJTvnZFzVvfAyq5MhHiScGfBz8XSJ9MUDrNlTU3ulEbSgqNJVWJx0IJ2oIkZtzHosd6LjB3dwkLggashixksJ3K_1iTM3-lsmEowuL-giROd6dY6GUEhCrpP00LSkJd8S5f5QwO-mHGhQ6uxCS2ydMW-adT9pYHodH4q2N5Q", "name": "Environmental Chemistry Inc", "rating": "NA", "id": "940f1e5d70276d8a5feaa5242d817666afa7f4b2", "job_title": "Ut-Health-Science-Center-At-Houston", "place_id": "ChIJ7UpnzJjqQIYR2qG-Hcvp_YU", "address": "2525 W Bellfort St Ste 175, Houston, TX 77054, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.57188149999999, 29.9951915], "type": "Point"}, "properties": {"photos": [{"width": 4785, "height": 3190, "html_attributions": ["<a href=\"https://maps.google.com/maps/contrib/101403699241874436061/photos\">Chemistry</a>"], "photo_reference": "CoQBdwAAANRlVBSrPEw28u5HgwMsr5SB2Z4EZe__zXprH7mo6VPI2OzNc2meM7ULMwIVGFNN6pkwSH_PbxHmHp8y5j5-SWy9_sC_tb5322OtJzqZ0g4_mhFgi082SniQznSxR635Gd8TjmI2Odku-08eAwRZpoKdzhmLEHphnbF4PPKR4iwNEhAn7OxlVM2b7qbfIjeB_6X5GhRD2tl9noHI0V4jK_Rsp__Zj3KT6A"}], "types": ["beauty_salon", "spa", "health", "clothing_store", "store", "point_of_interest", "establishment"], "reference": "CmRSAAAA96Ejkv4uEUu17gGPdFIUTqNLqxI7T0E3S2YL5c4EU6l-o7TD8LTptPnwDqGLYF168rnfQl46l5I6n1XHqUluUWC8hOh_aBzlaSI2E5yUbo48EFLHg7rju9q8oXoc0YGbEhCHCmDB1jqRGrL7Z-P5wCt6GhS5FQHhwGA67doTuRgxCcfLOB5PmQ", "name": "Chemistry", "rating": 5, "id": "979d392b613c49fbb954ee393bff65bda5042b34", "job_title": "Chamberlain-College-of-Nursing", "place_id": "ChIJWxsq_4fSQIYRU9dRPmk8uIw", "address": "126 Vintage Park Blvd N, Houston, TX 77070, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.34630229999999, 29.72187359999999], "type": "Point"}, "properties": {"photos": [{"width": 4160, "height": 3120, "html_attributions": ["<a href=\"https://maps.google.com/maps/contrib/108375995272754268174/photos\">Nitish Thareja</a>"], "photo_reference": "CoQBdwAAAGTMr8ZAuOdD8kLPiwKIkNxTaQqdjzvnciBs9qpb2-qDTXgTklEkxBMitzQuFCihGZraYFLW4fxEmD8RR_DcY-jTxo8HhSY4KfrEKSs0jMG2OOKc4On1vCDYhrew9F9ZxEqlOq0tROZN11AtC4bICqAJH5469VVHu7-t1r-uEoQaEhCcnhVGMgSKXuwIcCWoUKZXGhTlbZoiUJuk_tKgAbtLpHVY7jVE6Q"}], "types": ["point_of_interest", "establishment"], "reference": "CmRSAAAA5pIGg3l4Tu91ZV0g6SWJdjVxz0SgD6_nsfVmccKTdp0cxO442B6f6c_NRFdwqQ0FgD_4frB3UgDsyIoY8qMv_uLVwi83t7GCyIpyqGaxrqdhoXScG4zrqtQJjSbEz-LrEhCQc5kK8AsvpSWh3fZecKWqGhTBWyrvOiZR1AwfU-J-LYoZy7O6rg", "name": "University of Houston Department of Chemistry", "rating": 5, "id": "baa83832f81135d0180e7850ce768a11f32e9df5", "job_title": "Chamberlain-College-of-Nursing", "place_id": "ChIJgRkjS1G-QIYRmcpaGaD6ZeY", "address": "3585 Cullen Blvd #112, Houston, TX 77004, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.4025992, 29.7198268], "type": "Point"}, "properties": {"photos": [], "types": ["point_of_interest", "establishment"], "reference": "CmRSAAAAZAreXmcbB0hzNCN0uUZ_bDoqJgvnchckqZG7qS-L4RfHGYBfduarcsqTDJT09KF_LyLIJ4BFVmIS5uE5gcDnpMbvW3VSTU2PNewp2ReLwzLrzf2CngZNszg3uVyheJR6EhDtu0T-WpJlacqErwyDBTm9GhRjYPl3DbhhjFa3eoJBT3LxoMEidw", "name": "Rice University - Department of Chemistry", "rating": 3, "id": "1553681e69a2414f5cfa7551caa2102bc22268c1", "job_title": "Chamberlain-College-of-Nursing", "place_id": "ChIJL8yCnHzAQIYRZRcdAPRzhYI", "address": "6100 S Main St, Houston, TX 77005, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.4166517, 29.672442], "type": "Point"}, "properties": {"photos": [], "types": ["point_of_interest", "establishment"], "reference": "CmRSAAAAyMHiK8nb1mhCiDcJTvnZFzVvfAyq5MhHiScGfBz8XSJ9MUDrNlTU3ulEbSgqNJVWJx0IJ2oIkZtzHosd6LjB3dwkLggashixksJ3K_1iTM3-lsmEowuL-giROd6dY6GUEhCrpP00LSkJd8S5f5QwO-mHGhQ6uxCS2ydMW-adT9pYHodH4q2N5Q", "name": "Environmental Chemistry Inc", "rating": "NA", "id": "940f1e5d70276d8a5feaa5242d817666afa7f4b2", "job_title": "Chamberlain-College-of-Nursing", "place_id": "ChIJ7UpnzJjqQIYR2qG-Hcvp_YU", "address": "2525 W Bellfort St Ste 175, Houston, TX 77054, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.57188149999999, 29.9951915], "type": "Point"}, "properties": {"photos": [{"width": 4785, "height": 3190, "html_attributions": ["<a href=\"https://maps.google.com/maps/contrib/101403699241874436061/photos\">Chemistry</a>"], "photo_reference": "CoQBdwAAACtF-zfvAI0FdZLPHVmCsS8JhvZlYl40tnDlIp4zwqJNz3guxJCAGwSstpOQOGlbNWerROuMtHu_9f_Sz1dksMhkBMYYVh3xKsNgm8NJutKOn2Gno4RclsEVGe2pfi4isMScGJtGCGYZTzT43S-Rie16VmWYwW77lfFCPzrAZDRJEhAWDBQCqTUGBv-3-IXg8YkHGhTn49vJpWsoQJFnVoTDEZyVS1Orlw"}], "types": ["beauty_salon", "spa", "health", "clothing_store", "store", "point_of_interest", "establishment"], "reference": "CmRSAAAA8PMCDyJlcm1T4kkzUngKFUhWJRP-Zx219x2iLNxmtx9X7dT9ZxpAHGWumEm5eg5p4mRPIpbyBQ3OgGXYjFlhJzXJNwryU8n4Z8N3aSrKortXG9XftWFNixs-f-yVuZtHEhCL3LfQ4rosIA8J5YjEyrUaGhQUshryGMACc79gdQOU_GH_u4gGTA", "name": "Chemistry", "rating": 5, "id": "979d392b613c49fbb954ee393bff65bda5042b34", "job_title": "O%27rourke-Petroleum", "place_id": "ChIJWxsq_4fSQIYRU9dRPmk8uIw", "address": "126 Vintage Park Blvd N, Houston, TX 77070, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.34630229999999, 29.72187359999999], "type": "Point"}, "properties": {"photos": [{"width": 4160, "height": 3120, "html_attributions": ["<a href=\"https://maps.google.com/maps/contrib/108375995272754268174/photos\">Nitish Thareja</a>"], "photo_reference": "CoQBdwAAAF6Pm9J7YSO6oTJK1yjiFn700hyoJPORbpMSO1xys1ZycuAwkeimRdapdEpZuAvsbIoNsfehwsPRz6ZtGku4CqGZHOLKzhhqUpplkjgARwXHoFOtCViP5lxpInqbmOidpQSBdHdgqVYxCvaxoOlAbCtQpL7_nE-Tm2fGZYB4G_tWEhDxn9wF0UhR7wF5iXYX7jGoGhRkygy_wmkDgMrfol3HXY5y2XOdag"}], "types": ["point_of_interest", "establishment"], "reference": "CmRSAAAAGs9LbSgRBSW5Vwqc4oVu1NAHayoDs3rHlCZqPiPzcN0F6oDOWVL3NupxbI9KD6IZ6PS2sgIWV08Kx_UWf7Dd4KXtCMUSXX1-pi7GOkg651kTDFZrSrnhNIxZyFW_3Rz-EhDxNCayE1joCj0KC8rhKS0fGhStETXmsPf8gaC-JUDPZGVZ6_-IOQ", "name": "University of Houston Department of Chemistry", "rating": 5, "id": "baa83832f81135d0180e7850ce768a11f32e9df5", "job_title": "O%27rourke-Petroleum", "place_id": "ChIJgRkjS1G-QIYRmcpaGaD6ZeY", "address": "3585 Cullen Blvd #112, Houston, TX 77004, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.4025992, 29.7198268], "type": "Point"}, "properties": {"photos": [], "types": ["point_of_interest", "establishment"], "reference": "CmRSAAAAqvM_c8XTEkDzy6xB1U7Kvwq0V_Nczv9Ha8imYVfaStajq6JzV-EctRuqKYjiNS0xbxQ9VIKD1LkzdKo1J3MMxqCAXDIUdoNUGCwCO_LIP7uq7sqiF3DwvgwXlX_O0_a-EhC-a_8d6jTvKu_Pzl-RTwuFGhTLBLZw92lfPBCyIIzp6aXzGJW2pA", "name": "Rice University - Department of Chemistry", "rating": 3, "id": "1553681e69a2414f5cfa7551caa2102bc22268c1", "job_title": "O%27rourke-Petroleum", "place_id": "ChIJL8yCnHzAQIYRZRcdAPRzhYI", "address": "6100 S Main St, Houston, TX 77005, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.4166517, 29.672442], "type": "Point"}, "properties": {"photos": [], "types": ["point_of_interest", "establishment"], "reference": "CmRSAAAAo0NyCgLrD-o1ABy9vQX6w6zOWCC1J0wIYDuEdFvMiPqo0a0C9LF2oHjgfkwsSStuShq_e1ErZX92vArj_1q8RH_60T9vUp0b48eD0L9Wt2xi6kUuAIAVO_IRYlExoV_lEhBtyfpIaOMzHxLpc2TY-v7gGhSNboN9_EIQDuhz39if3Qz6zN-QRQ", "name": "Environmental Chemistry Inc", "rating": "NA", "id": "940f1e5d70276d8a5feaa5242d817666afa7f4b2", "job_title": "O%27rourke-Petroleum", "place_id": "ChIJ7UpnzJjqQIYR2qG-Hcvp_YU", "address": "2525 W Bellfort St Ste 175, Houston, TX 77054, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.57188149999999, 29.9951915], "type": "Point"}, "properties": {"photos": [{"width": 4785, "height": 3190, "html_attributions": ["<a href=\"https://maps.google.com/maps/contrib/101403699241874436061/photos\">Chemistry</a>"], "photo_reference": "CoQBdwAAAK7pnvI1o32q3aTqwYbfr3x6pt5FM0KtEDbyUCUQLz7cJ2_z4CwJg2am2vrnygzkHBUe1OBBdOJnSLCcztTk3uICgQtCi0kCh9MJOBU3nDPa1ztJFfItMrPPDa4yy5XlnJIKI8iq4r3JLZjy-zmsb9qG0RlCShUunNTlD_BDhoyPEhAi6ExovS-4OE9v-xEXTpAsGhQGKowJ3iWsVJRhuA5yS1FnkgXCww"}], "types": ["beauty_salon", "spa", "health", "clothing_store", "store", "point_of_interest", "establishment"], "reference": "CmRSAAAAvpE9ephYB4V2LP9lMPR0ZpYb0mHrnXHl4J66-07QiTFz0X3NEPUfhsrSBaiXnUyTNt5FpEHPDLjJTu0fdjxODg899Ko-CxNMoyMUrOAC4KRuTUuG5E27C_LKSFDLrZ_2EhCpb1Cf4uAMelSiplMFynEuGhSQUlmODXw3PHmloAkuHm4dMH2dUw", "name": "Chemistry", "rating": 5, "id": "979d392b613c49fbb954ee393bff65bda5042b34", "job_title": "Celanese", "place_id": "ChIJWxsq_4fSQIYRU9dRPmk8uIw", "address": "126 Vintage Park Blvd N, Houston, TX 77070, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.34630229999999, 29.72187359999999], "type": "Point"}, "properties": {"photos": [{"width": 4160, "height": 3120, "html_attributions": ["<a href=\"https://maps.google.com/maps/contrib/108375995272754268174/photos\">Nitish Thareja</a>"], "photo_reference": "CoQBdwAAAJXdw9pgNjv3CtiAS0GFLoLR4ZMiFMhLCJLVNUVbrPXKf0sxRDoO-LxSMtfOsGxVp-zUMNCLh0AfwTeT7fXi7YHpbF28ge7DBv2SFJUOJZKlKLvgZAJDGSc80CFoowJ5Z27fa8by749hpzAIqGDVTbjeMGBQ3hA0Bsr_w1ZRh0sUEhA-ETh_KqkFWpd10pgkdGlAGhSRzr83xooyUcV3p-KC_ahgZkrjXA"}], "types": ["point_of_interest", "establishment"], "reference": "CmRSAAAA9Yx0KEl9iwCaz0fCcR_ZrPqbh9f57sQSomoTjmxEawHebgi-r0GCaW8Sk6QpwIhtQT-BbGFkQqbbz5qsQrLANP9-XVMw4Iu_9E9My3ip9eytWqYRpmkk--ocR7T22-X5EhB0Xed1ee-WWvKUxweFosT-GhThJBVuWtSYxRo-goVSbU7YSHl52g", "name": "University of Houston Department of Chemistry", "rating": 5, "id": "baa83832f81135d0180e7850ce768a11f32e9df5", "job_title": "Celanese", "place_id": "ChIJgRkjS1G-QIYRmcpaGaD6ZeY", "address": "3585 Cullen Blvd #112, Houston, TX 77004, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.4025992, 29.7198268], "type": "Point"}, "properties": {"photos": [], "types": ["point_of_interest", "establishment"], "reference": "CmRSAAAAb8SE0b9-0FhggXSb4H0XZMFJtN95VmgDwUbhEH11pkmca-h2dCfw9nBrE9I_yczC2gdwK-eORfPs9yraND-f4yiQlBQQt4yhJE3TBt8fXo8ict4er7lIyCdZ9W3d1TaQEhCPWN4cDXEWT6nRGZ5nJmSNGhT6byvLifHlEFKa_1zYwqgvCVb3Ww", "name": "Rice University - Department of Chemistry", "rating": 3, "id": "1553681e69a2414f5cfa7551caa2102bc22268c1", "job_title": "Celanese", "place_id": "ChIJL8yCnHzAQIYRZRcdAPRzhYI", "address": "6100 S Main St, Houston, TX 77005, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.4166517, 29.672442], "type": "Point"}, "properties": {"photos": [], "types": ["point_of_interest", "establishment"], "reference": "CmRSAAAAbBMRDJbsVHjTO1AoLasYIYaf3cOECBUFBaF14yL2-tWdy_Opb5V5X04uMjnT1wczTxoBUYd2y0Xh6G2O-1LUsQ3neE_u_YhlSYIhV67J4qWjUBwy7kvgLvVlDNzhQ0dPEhB6zW-v9CQt-xOZ4i-fAH5_GhTDtJFAkzoevoV-Dnr8Ia_-k3qzbw", "name": "Environmental Chemistry Inc", "rating": "NA", "id": "940f1e5d70276d8a5feaa5242d817666afa7f4b2", "job_title": "Celanese", "place_id": "ChIJ7UpnzJjqQIYR2qG-Hcvp_YU", "address": "2525 W Bellfort St Ste 175, Houston, TX 77054, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.57188149999999, 29.9951915], "type": "Point"}, "properties": {"photos": [{"width": 4785, "height": 3190, "html_attributions": ["<a href=\"https://maps.google.com/maps/contrib/101403699241874436061/photos\">Chemistry</a>"], "photo_reference": "CoQBdwAAAFMDx89131W-4a0Lbq6h7VJAMBSK9FRABaDXI4rv4zYs01JDAd03tpVHcTw4aPiwHLSyTmVql4pbaDSsJ7gLD6b-ASaEbq45rqBGkXMSimTmeDha11iRnkFauBh-L1iPHa1xTsDwJQKHyocxQBm7MRxZQ662C2pgqlT9pSgVmW0eEhBxAsVh81VxEDN5MtuOZr1AGhS2AP3tBEmggTQoHcNCtCp1W0IbFQ"}], "types": ["beauty_salon", "spa", "health", "clothing_store", "store", "point_of_interest", "establishment"], "reference": "CmRSAAAAte5_oGuiq1EP71TLpQq5FfSc9qAZ4ZrhBnOemDjtHWxYI30Knexx4ulsSMIuV-qyXx4cm4uKQzUkfzaqpObj-t5JdYDiiy-jGgbL861R5d1u_2QmIjWnu39AVLT5XqlOEhCWY0sC2KjzERkHFvXECGvnGhQ0gowT9QtA7TfSEaXSiAGBRl3hyw", "name": "Chemistry", "rating": 5, "id": "979d392b613c49fbb954ee393bff65bda5042b34", "job_title": "O'rourke-Petroleum", "place_id": "ChIJWxsq_4fSQIYRU9dRPmk8uIw", "address": "126 Vintage Park Blvd N, Houston, TX 77070, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.34630229999999, 29.72187359999999], "type": "Point"}, "properties": {"photos": [{"width": 4160, "height": 3120, "html_attributions": ["<a href=\"https://maps.google.com/maps/contrib/108375995272754268174/photos\">Nitish Thareja</a>"], "photo_reference": "CoQBdwAAAEY3kCpgt_9xKwY5DVbS8E3hZy0MbYzUn4i01kwuWucrzlloFCiBs6lWtqrYuU93rNPhcc8cPpLzvw_C8Gif1MFDgFwoKOA_mRx9FHqigwh-YVPG2owVzQRXmLC17jAQKygiWKKcXI8YdEANYinsawVU69ZpIzEL5QB2WovIRsCjEhCssD1noJAvuRvGyOqUTYyIGhRJY0Nm9jeFnLZqGt2AajY5d4ubNw"}], "types": ["point_of_interest", "establishment"], "reference": "CmRSAAAAFI7E32tsWTCXp84uamq4TcepSGDbMO3oEQ_qtyWny4dT9jQBnfaZoGb2iPW0VeJr8yCkNmL2rwvCrfINYhhAjKhUcB37Sfuq4hSZVTO7NqaSGR59jX4w8_1vT_0a1FxOEhCKXf0pga2CRQW5WjN_Tr00GhQj2-PAyNUNgCFsE-6vt13af5XbzQ", "name": "University of Houston Department of Chemistry", "rating": 5, "id": "baa83832f81135d0180e7850ce768a11f32e9df5", "job_title": "O'rourke-Petroleum", "place_id": "ChIJgRkjS1G-QIYRmcpaGaD6ZeY", "address": "3585 Cullen Blvd #112, Houston, TX 77004, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.4025992, 29.7198268], "type": "Point"}, "properties": {"photos": [], "types": ["point_of_interest", "establishment"], "reference": "CmRSAAAAeJjfqX-K8a97G2sVa-SD7KrbcebH6BExcyjWIbIQ5ttiay4BHsrOEnlTy4tKmEzUAqVj7i75tSTV8X4sTpKv79X5p-8g42FfT9kjHFuAKEafUEGT7I8jPJ12Mjn1okymEhBqEPzpIEwDEJfm1mKY8qa5GhRJGM_fP5t7ex4Hj1uYVl8WVcgzNw", "name": "Rice University - Department of Chemistry", "rating": 3, "id": "1553681e69a2414f5cfa7551caa2102bc22268c1", "job_title": "O'rourke-Petroleum", "place_id": "ChIJL8yCnHzAQIYRZRcdAPRzhYI", "address": "6100 S Main St, Houston, TX 77005, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.4166517, 29.672442], "type": "Point"}, "properties": {"photos": [], "types": ["point_of_interest", "establishment"], "reference": "CmRSAAAAY6WmQh6Ax0-4M9BDngzjOzQHjWnosZmQfYYGU1prKBiRBnLkI67FoXCPNAGd61ziptOzSgc1SS8mdUbLySD3Gi5yFAz_9CEQ55BW0mh7btx1OHOTUfFzVqgLIBHwqJJQEhAn6PWar4btsvwqlvYIyICHGhTpciF2D7EPM2ARwWbBxjIutPEepQ", "name": "Environmental Chemistry Inc", "rating": "NA", "id": "940f1e5d70276d8a5feaa5242d817666afa7f4b2", "job_title": "O'rourke-Petroleum", "place_id": "ChIJ7UpnzJjqQIYR2qG-Hcvp_YU", "address": "2525 W Bellfort St Ste 175, Houston, TX 77054, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.57188149999999, 29.9951915], "type": "Point"}, "properties": {"photos": [{"width": 4785, "height": 3190, "html_attributions": ["<a href=\"https://maps.google.com/maps/contrib/101403699241874436061/photos\">Chemistry</a>"], "photo_reference": "CoQBdwAAACmhk7orBuhe6KCBpwYecna5of-7-YKvOMkE52vzOnYuU5QbWwBvAiCid_c6Q9pLbeB4TujMqumuZLrG9499BHH1HSISuojBxuak8ZR0zuNzQFL7V3GMzWnsIH8tsgY0bl3TS2p_z1iv2vXdIsINrtpv7Tdx06oiOaRY7TBfIHDnEhCMLNjKHa_ElBSpsnYSlQQfGhTFEjSoUjtJl0w0e356cxbSRTrXGA"}], "types": ["beauty_salon", "spa", "health", "clothing_store", "store", "point_of_interest", "establishment"], "reference": "CmRSAAAAx8qn8ParvNsP9eOClAmOC1hkMJSuQnfmxtdEWffrKNWGAf_A90ztcg93SsSVQ2dcPKC5NDYbGfAZTR0-_lq3hSjgztmjtFabjglsA325XQ51sqDWL5ZMecEOJc-Hv18FEhCjw9kYVAIGYyF2cgeIYJrIGhS9dK9kDh5pDVePgRKqD1_-LsMS_A", "name": "Chemistry", "rating": 5, "id": "979d392b613c49fbb954ee393bff65bda5042b34", "job_title": "Houston-Methodist", "place_id": "ChIJWxsq_4fSQIYRU9dRPmk8uIw", "address": "126 Vintage Park Blvd N, Houston, TX 77070, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.34630229999999, 29.72187359999999], "type": "Point"}, "properties": {"photos": [{"width": 4160, "height": 3120, "html_attributions": ["<a href=\"https://maps.google.com/maps/contrib/108375995272754268174/photos\">Nitish Thareja</a>"], "photo_reference": "CoQBdwAAAHPNpNVR5F1vRBTttWcgisPMZb2ceIg88UuRFBRCC6OJa_-MoBlZV23jnKN-_EELVA3rGqsng3jbfW7oC6MDTHNEidxtc5JRSBZECwGsXOrpGATuB9vDwD7yO-1GK2RxbWnWa6eRPp14pTLX7fzGBSGs-oaMU_4XjgYTVO07nnR6EhB8HLQYIJfxqmaURb4abb0NGhRZ8R-uUucReZXRaPWFF2tqnR1UDQ"}], "types": ["point_of_interest", "establishment"], "reference": "CmRSAAAA34eJcb2Jenj7GX7wrdWIbsAXYFpOnp7Lz3Y1Md-Ko3Ek73bwQfRFCogy0X0k4TJCIeu-CfMLlitmzXhRB4Us8JmKmd9U7daXXDlXt3-_nJ5J70E7yRk7SBym6Y_gmpxaEhB7Xr5AZWO6WgVsyB49YvaEGhTUGwmfBfqhf7t2ocph-L1bzkGLtA", "name": "University of Houston Department of Chemistry", "rating": 5, "id": "baa83832f81135d0180e7850ce768a11f32e9df5", "job_title": "Houston-Methodist", "place_id": "ChIJgRkjS1G-QIYRmcpaGaD6ZeY", "address": "3585 Cullen Blvd #112, Houston, TX 77004, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.4025992, 29.7198268], "type": "Point"}, "properties": {"photos": [], "types": ["point_of_interest", "establishment"], "reference": "CmRSAAAAJO1o2C35_sQHRXNhQ0e6NHSZyvE2JdXzCtDVNU-Ua1ILkbyrnFmg05bYyUjTPQ9p1CoFb_krvw5dR4QyTmM1Odi0y6ZunYOAiCaF0hrYnOMqwEcVumGjBH3L2GH9ECSoEhA7sljyPjJbGnbPhROAAhtdGhR06ZeWlZ49cXhsHe8DZK1Q1zvqgQ", "name": "Rice University - Department of Chemistry", "rating": 3, "id": "1553681e69a2414f5cfa7551caa2102bc22268c1", "job_title": "Houston-Methodist", "place_id": "ChIJL8yCnHzAQIYRZRcdAPRzhYI", "address": "6100 S Main St, Houston, TX 77005, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.4166517, 29.672442], "type": "Point"}, "properties": {"photos": [], "types": ["point_of_interest", "establishment"], "reference": "CmRSAAAATdCZTFFB6GZeNrRA3nCGNKLapQYm9B193__dT7JWCZ0MYgr9AXQ4CJ668af_DcL9FZCcosjsTRV2xg2z5qfAiVbNnG66ZzlZJLXJFvcKEjZQO7dGuqm2jgDhhdnwCCO6EhCyu5h11lpMmRfvD3scCgXnGhTWX2cVsiqceR0t8aC7YHrh7zTUoQ", "name": "Environmental Chemistry Inc", "rating": "NA", "id": "940f1e5d70276d8a5feaa5242d817666afa7f4b2", "job_title": "Houston-Methodist", "place_id": "ChIJ7UpnzJjqQIYR2qG-Hcvp_YU", "address": "2525 W Bellfort St Ste 175, Houston, TX 77054, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.57188149999999, 29.9951915], "type": "Point"}, "properties": {"photos": [{"width": 4785, "height": 3190, "html_attributions": ["<a href=\"https://maps.google.com/maps/contrib/101403699241874436061/photos\">Chemistry</a>"], "photo_reference": "CoQBdwAAABoHlXvdyQKLaQNf_6STkJMcs-T-Ha0ffB3nDlNfnV10i1tJgb-MGGUrPTPnGMxjWkkD0cbd5C82UQ8Kzp5vrXiDfh4FJja34cCp9hPedloSEF9h8p3hmZMrtOYUpnyd062bMIoHw3wEoZe2n0RyRB0iqUFIQCV6lYwSTSB4O9kEEhDcNAv8lEBEWRTi-5bLesZMGhSvSRwwD0CgFyZoWQ4Hj7LQ8OuoCA"}], "types": ["beauty_salon", "spa", "health", "clothing_store", "store", "point_of_interest", "establishment"], "reference": "CmRSAAAApxkEusSgNZs8q0TrHoZ42KseNRL7-EWOTXoou1KVap0QxCrM1QlQNTdFn3RYn7wj2D2o66SQpI5SCjKGnetX4iQ7-Ts0siOucok_c9CC6GioS52FGtA-fBlL1s_PrWbJEhDETnrOec1Bh_0tecOdv3UfGhQUEeP9Ry_PPhD0cDqqm-4S7ERN8Q", "name": "Chemistry", "rating": 5, "id": "979d392b613c49fbb954ee393bff65bda5042b34", "job_title": "Praxair", "place_id": "ChIJWxsq_4fSQIYRU9dRPmk8uIw", "address": "126 Vintage Park Blvd N, Houston, TX 77070, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.34630229999999, 29.72187359999999], "type": "Point"}, "properties": {"photos": [{"width": 4160, "height": 3120, "html_attributions": ["<a href=\"https://maps.google.com/maps/contrib/108375995272754268174/photos\">Nitish Thareja</a>"], "photo_reference": "CoQBdwAAAEVuOiqMhB3CZEyJ8AjN5Sz-2EWgEU65DEXL4WYGvr1i0oyOL8Q6kVKTzk5zEZa6-os83SwL8Zyf5BMzdpXXTekMQJ3ql0eQrJDFewt2nT4solvKgiQMbjup6W-4T92SfcTJgBGNObYo8GLuwKKrGlv0S61DlrnE5-Bjn3YY3EpREhDfsGuQSXYwbpDZzesPVMHoGhSBgRif5hxynhQx1lBvWTWGgve8vA"}], "types": ["point_of_interest", "establishment"], "reference": "CmRSAAAAAPtI_a49RGS-2lcdJj-ASsW27H0c08RJxngUR6LNVNyXpc1tf45O14o9ED_GCkPgO4gWzKZ0_Lcduh1TCpgIUmU8aUHFuUvpGpHLCbiAKN2ujlU3DSXyHJeMFSbQZZPLEhAY-cDliZ--CGVx5gDSwaFKGhSqqZPBKLdu5DYGl2hwmO5IAxm4XA", "name": "University of Houston Department of Chemistry", "rating": 5, "id": "baa83832f81135d0180e7850ce768a11f32e9df5", "job_title": "Praxair", "place_id": "ChIJgRkjS1G-QIYRmcpaGaD6ZeY", "address": "3585 Cullen Blvd #112, Houston, TX 77004, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.4025992, 29.7198268], "type": "Point"}, "properties": {"photos": [], "types": ["point_of_interest", "establishment"], "reference": "CmRSAAAAYK1Z9BMQuZ0GjX0wO6QGODZT218D4FkpcroaUwY2Uq9Irt6uv7hZy8qxfajuAKJUfBtvg4Oxsj92xPznbNU_GZKiQUXEibgPHwcfigquGBn3yN0syzaHMGabOPPgPBrsEhC5NuonrGfe7G6HWi9KtC8lGhR_fNiAw2UhIy73NTE5nwgdi1EFEA", "name": "Rice University - Department of Chemistry", "rating": 3, "id": "1553681e69a2414f5cfa7551caa2102bc22268c1", "job_title": "Praxair", "place_id": "ChIJL8yCnHzAQIYRZRcdAPRzhYI", "address": "6100 S Main St, Houston, TX 77005, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.4166517, 29.672442], "type": "Point"}, "properties": {"photos": [], "types": ["point_of_interest", "establishment"], "reference": "CmRSAAAAIFVOHeHkAgvMMjHB9xWWexfqt-TINcz2OyJP7b5LoOBc0IZlDsymg4TfjIxmlxoe2eEbqB6Kl856fAQ1kf5SFYyR8fgSTrA_Tnd2k0WCvB3_K-oigKLaWlHwSHGl-HUFEhBNo-du7ddnL5jPtSc2uCysGhSL7lhf6iYP9XYxHWT-ergsnQIk3A", "name": "Environmental Chemistry Inc", "rating": "NA", "id": "940f1e5d70276d8a5feaa5242d817666afa7f4b2", "job_title": "Praxair", "place_id": "ChIJ7UpnzJjqQIYR2qG-Hcvp_YU", "address": "2525 W Bellfort St Ste 175, Houston, TX 77054, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.57188149999999, 29.9951915], "type": "Point"}, "properties": {"photos": [{"width": 4785, "height": 3190, "html_attributions": ["<a href=\"https://maps.google.com/maps/contrib/101403699241874436061/photos\">Chemistry</a>"], "photo_reference": "CoQBdwAAANRlVBSrPEw28u5HgwMsr5SB2Z4EZe__zXprH7mo6VPI2OzNc2meM7ULMwIVGFNN6pkwSH_PbxHmHp8y5j5-SWy9_sC_tb5322OtJzqZ0g4_mhFgi082SniQznSxR635Gd8TjmI2Odku-08eAwRZpoKdzhmLEHphnbF4PPKR4iwNEhAn7OxlVM2b7qbfIjeB_6X5GhRD2tl9noHI0V4jK_Rsp__Zj3KT6A"}], "types": ["beauty_salon", "spa", "health", "clothing_store", "store", "point_of_interest", "establishment"], "reference": "CmRSAAAA96Ejkv4uEUu17gGPdFIUTqNLqxI7T0E3S2YL5c4EU6l-o7TD8LTptPnwDqGLYF168rnfQl46l5I6n1XHqUluUWC8hOh_aBzlaSI2E5yUbo48EFLHg7rju9q8oXoc0YGbEhCHCmDB1jqRGrL7Z-P5wCt6GhS5FQHhwGA67doTuRgxCcfLOB5PmQ", "name": "Chemistry", "rating": 5, "id": "979d392b613c49fbb954ee393bff65bda5042b34", "job_title": "Solvay", "place_id": "ChIJWxsq_4fSQIYRU9dRPmk8uIw", "address": "126 Vintage Park Blvd N, Houston, TX 77070, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.34630229999999, 29.72187359999999], "type": "Point"}, "properties": {"photos": [{"width": 4160, "height": 3120, "html_attributions": ["<a href=\"https://maps.google.com/maps/contrib/108375995272754268174/photos\">Nitish Thareja</a>"], "photo_reference": "CoQBdwAAAGTMr8ZAuOdD8kLPiwKIkNxTaQqdjzvnciBs9qpb2-qDTXgTklEkxBMitzQuFCihGZraYFLW4fxEmD8RR_DcY-jTxo8HhSY4KfrEKSs0jMG2OOKc4On1vCDYhrew9F9ZxEqlOq0tROZN11AtC4bICqAJH5469VVHu7-t1r-uEoQaEhCcnhVGMgSKXuwIcCWoUKZXGhTlbZoiUJuk_tKgAbtLpHVY7jVE6Q"}], "types": ["point_of_interest", "establishment"], "reference": "CmRSAAAA5pIGg3l4Tu91ZV0g6SWJdjVxz0SgD6_nsfVmccKTdp0cxO442B6f6c_NRFdwqQ0FgD_4frB3UgDsyIoY8qMv_uLVwi83t7GCyIpyqGaxrqdhoXScG4zrqtQJjSbEz-LrEhCQc5kK8AsvpSWh3fZecKWqGhTBWyrvOiZR1AwfU-J-LYoZy7O6rg", "name": "University of Houston Department of Chemistry", "rating": 5, "id": "baa83832f81135d0180e7850ce768a11f32e9df5", "job_title": "Solvay", "place_id": "ChIJgRkjS1G-QIYRmcpaGaD6ZeY", "address": "3585 Cullen Blvd #112, Houston, TX 77004, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.4025992, 29.7198268], "type": "Point"}, "properties": {"photos": [], "types": ["point_of_interest", "establishment"], "reference": "CmRSAAAAZAreXmcbB0hzNCN0uUZ_bDoqJgvnchckqZG7qS-L4RfHGYBfduarcsqTDJT09KF_LyLIJ4BFVmIS5uE5gcDnpMbvW3VSTU2PNewp2ReLwzLrzf2CngZNszg3uVyheJR6EhDtu0T-WpJlacqErwyDBTm9GhRjYPl3DbhhjFa3eoJBT3LxoMEidw", "name": "Rice University - Department of Chemistry", "rating": 3, "id": "1553681e69a2414f5cfa7551caa2102bc22268c1", "job_title": "Solvay", "place_id": "ChIJL8yCnHzAQIYRZRcdAPRzhYI", "address": "6100 S Main St, Houston, TX 77005, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.4166517, 29.672442], "type": "Point"}, "properties": {"photos": [], "types": ["point_of_interest", "establishment"], "reference": "CmRSAAAAyMHiK8nb1mhCiDcJTvnZFzVvfAyq5MhHiScGfBz8XSJ9MUDrNlTU3ulEbSgqNJVWJx0IJ2oIkZtzHosd6LjB3dwkLggashixksJ3K_1iTM3-lsmEowuL-giROd6dY6GUEhCrpP00LSkJd8S5f5QwO-mHGhQ6uxCS2ydMW-adT9pYHodH4q2N5Q", "name": "Environmental Chemistry Inc", "rating": "NA", "id": "940f1e5d70276d8a5feaa5242d817666afa7f4b2", "job_title": "Solvay", "place_id": "ChIJ7UpnzJjqQIYR2qG-Hcvp_YU", "address": "2525 W Bellfort St Ste 175, Houston, TX 77054, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.57188149999999, 29.9951915], "type": "Point"}, "properties": {"photos": [{"width": 4785, "height": 3190, "html_attributions": ["<a href=\"https://maps.google.com/maps/contrib/101403699241874436061/photos\">Chemistry</a>"], "photo_reference": "CoQBdwAAAMH18ln03FhaLitNRr8dJSV84pDnj8L3KwyxQkCc8MIIBcDFSjBE3s7ijcooTRVbbvly-tzBysE94J5XRY7VBU8i8Bjq61jt4F-Cnu6XSVruh1180cM1FY_dHbUVqfAyNert6MieI0UTL5D_zHuWEW7EghPzCWxEW5R78yKjRMTrEhAbukm5x-vPKugbuXK1UT55GhRZe_farivmkMlhrz1AIkW2kjQgeA"}], "types": ["beauty_salon", "spa", "health", "clothing_store", "store", "point_of_interest", "establishment"], "reference": "CmRSAAAAl_QPuYdIoURTwT453PT4rdZ3ZziyhlfcstdlHHnQ10scBN3lfM_EugsrhTQBQ6QF9FSUTnV-knp9Gc75kjXjfCHvs_4jaX3QUxY1lSUWxzAMbz7yRdX61E8FRS0IGKdIEhCVNvHVaA6I-7Lesgan_rpOGhQ_vXcPQdhb2dXVCSjzgSVxFsHYGg", "name": "Chemistry", "rating": 5, "id": "979d392b613c49fbb954ee393bff65bda5042b34", "job_title": "Sgs", "place_id": "ChIJWxsq_4fSQIYRU9dRPmk8uIw", "address": "126 Vintage Park Blvd N, Houston, TX 77070, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.34630229999999, 29.72187359999999], "type": "Point"}, "properties": {"photos": [{"width": 4160, "height": 3120, "html_attributions": ["<a href=\"https://maps.google.com/maps/contrib/108375995272754268174/photos\">Nitish Thareja</a>"], "photo_reference": "CoQBdwAAACXnkdkgIeS6h896BGyGw3ad8-L3TvZvzCkWG2f7h8IZh5YGnRQ2ClqwvuTtEkoTHWnLAufATawedUPgCHafNEB_gPxDnPi4Rq3BayIUUtbmvKafGdmgnbDAFvs1UxrkOxBPmKCc08mikib_s3Zn-n93JGQ2nWfu8rg4vohsleT3EhCFe-lyJq3Uji8KrTGsZwVhGhQ6yL7R9GC3oLf1qdl44YK5Cv-8GA"}], "types": ["point_of_interest", "establishment"], "reference": "CmRSAAAAJ4k3WSMNDkcHm3FIa082bewXYXxx1sx5dQTptkLnfmrh0IPhdJwUAcLM_dVB8tivTq3Qs2X0LcGNyggAlCki3kCvkSEeSnOrMASPbbjJTP4CFNSjPsYVPr1e_jzNHvaVEhCwKVPB9KGfdqD8sfPiX2jJGhSFPwvyvasdVpCSx8OUos8Ipdm7YA", "name": "University of Houston Department of Chemistry", "rating": 5, "id": "baa83832f81135d0180e7850ce768a11f32e9df5", "job_title": "Sgs", "place_id": "ChIJgRkjS1G-QIYRmcpaGaD6ZeY", "address": "3585 Cullen Blvd #112, Houston, TX 77004, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.4025992, 29.7198268], "type": "Point"}, "properties": {"photos": [], "types": ["point_of_interest", "establishment"], "reference": "CmRSAAAANbiJ63r4fBhfx3LypTT-rzKQp_NRaRBL_HcyZwqePvKxxOOfBdTKySpcLDVi_1gP8DbZTP0_qo2ycWVTFxswq8BPL0qPu4oN0saFrGmaiFyPzpCA3nivwYiXWiKLl7JzEhCIcU-GkVACMSXBjfbwQ12pGhTRPX6x1WvV96lWMcqCoypt8cXQuQ", "name": "Rice University - Department of Chemistry", "rating": 3, "id": "1553681e69a2414f5cfa7551caa2102bc22268c1", "job_title": "Sgs", "place_id": "ChIJL8yCnHzAQIYRZRcdAPRzhYI", "address": "6100 S Main St, Houston, TX 77005, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.4166517, 29.672442], "type": "Point"}, "properties": {"photos": [], "types": ["point_of_interest", "establishment"], "reference": "CmRSAAAAQ4-suqxBpKY8v2R7zeFpFydA-PBsgmPHHkxDLMgOoljbOdTB7NhBTqqCy80zTn-3nZHXp4xlhmaFeRBedMfpuNGVbrOCIInlPSzeTtyG6v1aTIpdB2P_-GGlBVXhu4_fEhCcO4VA7JAHCkYme4Qs1fTrGhR484DEa3GoKj0_ZtshjfEW0HD1Dg", "name": "Environmental Chemistry Inc", "rating": "NA", "id": "940f1e5d70276d8a5feaa5242d817666afa7f4b2", "job_title": "Sgs", "place_id": "ChIJ7UpnzJjqQIYR2qG-Hcvp_YU", "address": "2525 W Bellfort St Ste 175, Houston, TX 77054, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.57188149999999, 29.9951915], "type": "Point"}, "properties": {"photos": [{"width": 4785, "height": 3190, "html_attributions": ["<a href=\"https://maps.google.com/maps/contrib/101403699241874436061/photos\">Chemistry</a>"], "photo_reference": "CoQBdwAAAD0rhgkRF_77GceTy53fYov222-BH9rzKuAd7c4W34MnZpke7QKFL7M9DRdLlKfHmuJsTJ1ef2UOxwdYxyabgEooqI0vED71EkvdEbN4qxW020p7EKKjdCj8_llSF4cZS802Fd-GA3UeDhNJihv1_msJ6veKrvTH7H51NbxhUec0EhAnd5k400xAhhfcStru57kdGhQbWOivYOCvhcv_BxC5-7xJ4GKDkg"}], "types": ["beauty_salon", "spa", "health", "clothing_store", "store", "point_of_interest", "establishment"], "reference": "CmRSAAAAvOKsHDWDiEBOwcZFKyQU0q__XoO3s1lh6Dx7RbpyCUt3QrXJNGY8ErZTmVSQ4Bf5GIUZdeDYb9UZdbvYr9g-2rlYpRk-Ct1cQbHv1bydXfJhWmdGkK_ausFzdWcX4IJGEhCFnwJ7su8UMVzHbrzMneXjGhTg4N_XbbxqQ80pLZK2SLEpG94MUQ", "name": "Chemistry", "rating": 5, "id": "979d392b613c49fbb954ee393bff65bda5042b34", "job_title": "Nalco-Champion,-An-Ecolab-Company", "place_id": "ChIJWxsq_4fSQIYRU9dRPmk8uIw", "address": "126 Vintage Park Blvd N, Houston, TX 77070, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.34630229999999, 29.72187359999999], "type": "Point"}, "properties": {"photos": [{"width": 4160, "height": 3120, "html_attributions": ["<a href=\"https://maps.google.com/maps/contrib/108375995272754268174/photos\">Nitish Thareja</a>"], "photo_reference": "CoQBdwAAAPya2HgINBR5aBeUfUch6AFJsEHuV6LmE-Acix9GsgNSQqug6zPvI8_W8ZD_vkznam_aGXOisnG4wC7GVPSC9QYpQpcKejk4QzyXfMQupyDaU1URFcajc3BgqgmrclDFEQWh_-Rfr2WcA9LVL-SshP-X2IXlI_31oLhNWm5iSCmEEhClUnASsPxAX4gnO--HP0G4GhT5DTP7mateT4Q_O3GVxZvLOSnx9A"}], "types": ["point_of_interest", "establishment"], "reference": "CmRSAAAApRqGMcmD6047HmoczU8jrxI9vtupQ0WxWbygk9wipDq40P8rQYrA5wC2ntP08Rzvqb8qKTtDgq_DedaUHrchQMkXajEmiugwhE5UFOYA-zY_UudLfLZ4YFz3jZzfeKN0EhCUIrTqoigXtE1A93tWtJGXGhRtPf8-TEwCTtqThxiwBOEnIh5R_Q", "name": "University of Houston Department of Chemistry", "rating": 5, "id": "baa83832f81135d0180e7850ce768a11f32e9df5", "job_title": "Nalco-Champion,-An-Ecolab-Company", "place_id": "ChIJgRkjS1G-QIYRmcpaGaD6ZeY", "address": "3585 Cullen Blvd #112, Houston, TX 77004, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.4025992, 29.7198268], "type": "Point"}, "properties": {"photos": [], "types": ["point_of_interest", "establishment"], "reference": "CmRSAAAAy-h4F3eH3orULfjEGLbXQt9lC5XC6V9lM34UTtd4e7CN1KfsinLq8X9Kx6-qdZtJaCxMotUEttEEeI39vpgAxqFlCKPWVhx_2nu2HbS72dujLo2tZpEElh89PrIHyC9zEhDkf14-_0AerJN7dlkmURwZGhRXxXGRYphbiB-PKhyxQXkhCgrvqg", "name": "Rice University - Department of Chemistry", "rating": 3, "id": "1553681e69a2414f5cfa7551caa2102bc22268c1", "job_title": "Nalco-Champion,-An-Ecolab-Company", "place_id": "ChIJL8yCnHzAQIYRZRcdAPRzhYI", "address": "6100 S Main St, Houston, TX 77005, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.4166517, 29.672442], "type": "Point"}, "properties": {"photos": [], "types": ["point_of_interest", "establishment"], "reference": "CmRSAAAAELwsPLEplMAeYzV9nvgF_An6bSuRZU8l9ZEGjihKPrCNqUdFpzpA11BOZe-StNpWShkd4K_jErwLxf2UYoiQH6f_VJhpO3jt6Iux82yuN7-9BudOLRT7G_uJadd940P8EhAMnY9rinhjDwWhZP2pATOnGhRcJUIaKJwhNy_BQ6Ct6V1YgWSLoQ", "name": "Environmental Chemistry Inc", "rating": "NA", "id": "940f1e5d70276d8a5feaa5242d817666afa7f4b2", "job_title": "Nalco-Champion,-An-Ecolab-Company", "place_id": "ChIJ7UpnzJjqQIYR2qG-Hcvp_YU", "address": "2525 W Bellfort St Ste 175, Houston, TX 77054, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.57188149999999, 29.9951915], "type": "Point"}, "properties": {"photos": [{"width": 4785, "height": 3190, "html_attributions": ["<a href=\"https://maps.google.com/maps/contrib/101403699241874436061/photos\">Chemistry</a>"], "photo_reference": "CoQBdwAAAO0JW2Bj4Z8IK4pqq7e6cc-GGZ7IDS1v-wVrS3idXQd5gilooLwkBj4Nq7TUV9-5fu_BHeLNEPh4vbeymx_ql8FJLPVZsv04EA-yBIbJUITT7tWnXFxBYV_y4OJ2ivIMF5q8ecYM4d39P4UkEAheyOBNzuhre6-KQJVCx-mZUbLnEhBPkjT_P12GJWuqobY2EaWRGhSvh9QFB2Of4PvUxeXJa2KbxV_fOw"}], "types": ["beauty_salon", "spa", "health", "clothing_store", "store", "point_of_interest", "establishment"], "reference": "CmRSAAAAMGZumzKMwkaTLRchTs-Fz0Fz4NM5xYeXgHvswypBsRzHoVtURsuOsbT-OtoXit1eMDmTXN_bwxjsJ4rINGLt7dIcPEEw2B6DOAeBzHfvN4Blr0v988SjTipFHGstfhNMEhAVEAB9ipmSkOtzuR5lpNrQGhRioX0478ApHRCyyoFlrrswKiieZQ", "name": "Chemistry", "rating": 5, "id": "979d392b613c49fbb954ee393bff65bda5042b34", "job_title": "Schlumberger", "place_id": "ChIJWxsq_4fSQIYRU9dRPmk8uIw", "address": "126 Vintage Park Blvd N, Houston, TX 77070, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.34630229999999, 29.72187359999999], "type": "Point"}, "properties": {"photos": [{"width": 4160, "height": 3120, "html_attributions": ["<a href=\"https://maps.google.com/maps/contrib/108375995272754268174/photos\">Nitish Thareja</a>"], "photo_reference": "CoQBdwAAAOiF0VHJoof_Krp1LljNxtCEonNpktgw4a6NFGnVngBvOLy8JVUxfyJm07JumCBjy3Rm4bVP26uiz3FYwBiaFP7oF9YIBAjSmTgtZbYtbdb4MGHxOomi-HHMOlMCzYv4zGIE2ZjbdxntPoEzWcCFBqibYLyx7wInFopWMC7byonhEhDLuzAzAhfBJFyusXkEk7YfGhSgKAwXv_3ZdyEDSrhGNAmZxSMw0g"}], "types": ["point_of_interest", "establishment"], "reference": "CmRSAAAAspvJB5qGziKyyzPcOhexCmJ1kvpAg4qxIf73B2IyeEU6KOpJKOm5lbAq23UHzjEf2ThOZ9lvcMZHAjCkU4JfFSOLS0EqnYJ2pGQAsUB6RGYkTAul4oxOJnE8o4rE4L9jEhBLtUuuQL_A2qKoWFuTvxnsGhSnD4Ygse9Y7bb7RPyByqvaIk01pw", "name": "University of Houston Department of Chemistry", "rating": 5, "id": "baa83832f81135d0180e7850ce768a11f32e9df5", "job_title": "Schlumberger", "place_id": "ChIJgRkjS1G-QIYRmcpaGaD6ZeY", "address": "3585 Cullen Blvd #112, Houston, TX 77004, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.4025992, 29.7198268], "type": "Point"}, "properties": {"photos": [], "types": ["point_of_interest", "establishment"], "reference": "CmRSAAAA6h6oTWsj4tLJ5nArUWB9n-WJpEzJd64Ys9c3XM3oh1WLHWs_mpe01axd_ETuv4USX2Iz_tO31J5ysb9mC1fb49i_qgpqtSDc1vnQ2E9BSHsN8KPwifZAoWJCElVAbs1KEhC166DN-btgIiDoTVT3x0pUGhSMkMYplyxYkHm9Et7oku9KXIVkIQ", "name": "Rice University - Department of Chemistry", "rating": 3, "id": "1553681e69a2414f5cfa7551caa2102bc22268c1", "job_title": "Schlumberger", "place_id": "ChIJL8yCnHzAQIYRZRcdAPRzhYI", "address": "6100 S Main St, Houston, TX 77005, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.4166517, 29.672442], "type": "Point"}, "properties": {"photos": [], "types": ["point_of_interest", "establishment"], "reference": "CmRSAAAAzkcbo-PpG8OSP2ZEnESyoCwPRrcaRq15hRA2RmOqsV61K261tITqiEril9g_ujBGpo2BKkW8tyEk3vLKNDZoSIOuZpXTdzih1jjotAC8gYancm__M0yptfdX9KiK1nTUEhASiuYszMbvv6MSo0stF2CmGhTDOyns8cVicnW1VgNA8zUP7U4DSw", "name": "Environmental Chemistry Inc", "rating": "NA", "id": "940f1e5d70276d8a5feaa5242d817666afa7f4b2", "job_title": "Schlumberger", "place_id": "ChIJ7UpnzJjqQIYR2qG-Hcvp_YU", "address": "2525 W Bellfort St Ste 175, Houston, TX 77054, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.57188149999999, 29.9951915], "type": "Point"}, "properties": {"photos": [{"width": 4785, "height": 3190, "html_attributions": ["<a href=\"https://maps.google.com/maps/contrib/101403699241874436061/photos\">Chemistry</a>"], "photo_reference": "CoQBdwAAAK7mKIjNEpTTkfMg61px3XUsqmQxmvNbjCy-y4tM7Ywhi2k2MLxyq9bthZFydzWgoWPQi-xPkxnIqN_NtqeYaj3Y9sqMxbAImJ7IIa_-_ok4WJa2xyt__gK-IEQMXKH0kHcDejEhiPd8mVQG0lAWRdpLtC0yJhKqQFPwizRCPWbPEhAVbEz5aqBaOnThfjSV_LxpGhQ3wdPUS26MI6RE-1kxcq2AzS73gw"}], "types": ["beauty_salon", "spa", "health", "clothing_store", "store", "point_of_interest", "establishment"], "reference": "CmRSAAAA3-8L6MaKw5m4Z-7hKUz4Ul0kvWHs5arOyd59mKNErPaAG3uXjBSRk7CfkWWzAGaBRHzTgLfdN6OLSpBpse1rVhSpDwRQTsh0bKGZwjhbgFahQP7gv8hH_yR4MduQ2nPWEhB4yNXKRXvfDK-D7ANJlwUqGhR7tJHxhepq_H6oazMT9gLODR3KSQ", "name": "Chemistry", "rating": 5, "id": "979d392b613c49fbb954ee393bff65bda5042b34", "job_title": "Exxonmobil", "place_id": "ChIJWxsq_4fSQIYRU9dRPmk8uIw", "address": "126 Vintage Park Blvd N, Houston, TX 77070, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.34630229999999, 29.72187359999999], "type": "Point"}, "properties": {"photos": [{"width": 4160, "height": 3120, "html_attributions": ["<a href=\"https://maps.google.com/maps/contrib/108375995272754268174/photos\">Nitish Thareja</a>"], "photo_reference": "CoQBdwAAAK0mYW9eVyIIAdi3TPiDjnmm0Ly9u8oVnoxw68NjUFo_XBtaQap4Eetzr1HW0zZ39cO9YhE0ScA7zVb04eiy4t16wbevNIgbiIES99lBL2QZG9CnXsAMW4uQgRoatM8rsbtL-TU6Wz1VJRZ9IoMduV3T--bLBIt3FfrtDmWxPA9WEhBh3UEfSybg2coS1xfgz37SGhSIKbmzPm8wh-4NqERmsHq3OciXcw"}], "types": ["point_of_interest", "establishment"], "reference": "CmRSAAAAXsyWyMr329CnV_sx1ZuNCui-jDgz6_PvxQdT3JEZq1GwR4x02QjnVJ-o6EocA4pS1Wc131LY3OF1djUStYGg6rgzc_ZZ--Ffop0-gvEuiV_qUgEDopWPAN4txmyCXrDSEhBAhq1CZazjib6ZCG-eCL7iGhRy0i13PzaGUZ0mCQQN2-iHiNACfg", "name": "University of Houston Department of Chemistry", "rating": 5, "id": "baa83832f81135d0180e7850ce768a11f32e9df5", "job_title": "Exxonmobil", "place_id": "ChIJgRkjS1G-QIYRmcpaGaD6ZeY", "address": "3585 Cullen Blvd #112, Houston, TX 77004, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.4025992, 29.7198268], "type": "Point"}, "properties": {"photos": [], "types": ["point_of_interest", "establishment"], "reference": "CmRSAAAAdL1hLwnatdoBd5ImwBcqmQRWGuYprhOC7a6zCZ8DUitam1aISrMnGGcyY_5d_k2ll1JB2oStVTx9Hugffy5BGLJqPEw0YlbFhPztVvVEAyhdh8Lxj9T5_oai9FJfS91rEhBcSz0vBM78DrIMP_7_qSOYGhR51FI7biiT_gbiCFGaDmlQrv7m7A", "name": "Rice University - Department of Chemistry", "rating": 3, "id": "1553681e69a2414f5cfa7551caa2102bc22268c1", "job_title": "Exxonmobil", "place_id": "ChIJL8yCnHzAQIYRZRcdAPRzhYI", "address": "6100 S Main St, Houston, TX 77005, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.4166517, 29.672442], "type": "Point"}, "properties": {"photos": [], "types": ["point_of_interest", "establishment"], "reference": "CmRSAAAAEEn1kfNMDmoYMJRKQcCbxFhUuDqIn49tUim7_oMjMQP0T1028s1UWOYlfH04tL2jo9wsgXQPVonQLIMlIH8nzC7ZmxGop-Imffbyubyus5wu7z0Bw0GY0fJWHsW8O1-QEhASCIw7FYZMU_lnT2frtcwnGhTG_Nv8DxvQ3p-uwj_tu2iDgEK_Ng", "name": "Environmental Chemistry Inc", "rating": "NA", "id": "940f1e5d70276d8a5feaa5242d817666afa7f4b2", "job_title": "Exxonmobil", "place_id": "ChIJ7UpnzJjqQIYR2qG-Hcvp_YU", "address": "2525 W Bellfort St Ste 175, Houston, TX 77054, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.57188149999999, 29.9951915], "type": "Point"}, "properties": {"photos": [{"width": 4785, "height": 3190, "html_attributions": ["<a href=\"https://maps.google.com/maps/contrib/101403699241874436061/photos\">Chemistry</a>"], "photo_reference": "CoQBdwAAAAmSE6V5t9lqIxGo5a1QTiuTpbkujy9n2RMgAlKNkhxAJWXUSR__VAbKCnLvYlSfb_VyrpcLyyHb6D9upsSvRwuVG82Wm4UwhFVlmr6rhvGjLeX79wxL1dJP6X9ejcxPYshA4JVwc1gMjs8g25-FFvheT0ENi94cRDdozeqUIb0hEhBPrj-AaubL-4ci1gqfo368GhQqJRHC4G7wD15TFUf9Mv0MGWtGkg"}], "types": ["beauty_salon", "spa", "health", "clothing_store", "store", "point_of_interest", "establishment"], "reference": "CmRSAAAAJOFi31LyfjEYaBcVLlRhxO3ZettIWgiesikQv1RESQ49pEFt_Uf1Bo3HPRFlhXHrV8C9hW7oKQbBUo6aXSWY3CEwoyWebWnGbUOp0g5qG7H952KZsJ9yZatDzDcigVELEhBHmyjF9borxAAMJoaGoIN-GhSpRYAiIWMEpx4RZCONLy5d0BSn-g", "name": "Chemistry", "rating": 5, "id": "979d392b613c49fbb954ee393bff65bda5042b34", "job_title": "Stericycle", "place_id": "ChIJWxsq_4fSQIYRU9dRPmk8uIw", "address": "126 Vintage Park Blvd N, Houston, TX 77070, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.34630229999999, 29.72187359999999], "type": "Point"}, "properties": {"photos": [{"width": 4160, "height": 3120, "html_attributions": ["<a href=\"https://maps.google.com/maps/contrib/108375995272754268174/photos\">Nitish Thareja</a>"], "photo_reference": "CoQBdwAAAC5oUKocIjtEX1BOEcZ2TLwhoPCWWdVHcDtYD1q4hSP8rT51kxSwLugGh5zBE8kAukXgm1zsaxVvqBg6H1MHxmlfCHbqVp1ZLnMlENx0nliK53b6MHcLdNmZM3mXncjZDp_yC32K4axnMqdDTurg5j-qBZbXVa6YPaqnJ0z6bQGSEhBHcGuQIYiUJvCHByhDl3hRGhQSVf4I86icpuUAmzyCLg0YbHBRjA"}], "types": ["point_of_interest", "establishment"], "reference": "CmRSAAAAmv3L-e6SSAivfbquZakm62AuDht-HB9CfP_wgP7VCMNm8cc1_g9rEE8qWWWL34swCPpqnzUnGNbpqI_VOHXp4xiMKwOCXRLURbwFKgx2EdFvm2w-MyvjRs1WOvhEIXl9EhBDHVA6HZQ5MZD9cK5NtgpJGhRFRZg60MzhoJoVUf5SD9TFoO1k0A", "name": "University of Houston Department of Chemistry", "rating": 5, "id": "baa83832f81135d0180e7850ce768a11f32e9df5", "job_title": "Stericycle", "place_id": "ChIJgRkjS1G-QIYRmcpaGaD6ZeY", "address": "3585 Cullen Blvd #112, Houston, TX 77004, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.4025992, 29.7198268], "type": "Point"}, "properties": {"photos": [], "types": ["point_of_interest", "establishment"], "reference": "CmRSAAAASWU5lJf4STCLV_QiVrKQkbnS2FGxdZWId_oC7Q_TMpHa0pttRVFBbHsfn40g4RPOOfgJb1Z9emulw43PZQmPU3EHPlvmByerVsfxlTBHV2z2lO_h1uSqB62-Y30N3gn0EhCduPCrdDoCD_m2kyzPo3ytGhTfqT2uNoAmsothdVr0MUBhcSUmsA", "name": "Rice University - Department of Chemistry", "rating": 3, "id": "1553681e69a2414f5cfa7551caa2102bc22268c1", "job_title": "Stericycle", "place_id": "ChIJL8yCnHzAQIYRZRcdAPRzhYI", "address": "6100 S Main St, Houston, TX 77005, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.4166517, 29.672442], "type": "Point"}, "properties": {"photos": [], "types": ["point_of_interest", "establishment"], "reference": "CmRSAAAA40NYUBkdBznUcEo8a0xihZmU9BsfD5HypC9V9kd-nYdtX__7JBzaONmJ9IlshHqk5DqTJeeIX_7ZAyqopvjWsrM9SKi_PmIs-q2B7wXMtXU3fl4zSjAf_oXmxyZRUOjnEhDjTFV2vPBlj0jEN4YwIgYSGhTdA1aKKO8zkcmsbpHQv3uneqPSFw", "name": "Environmental Chemistry Inc", "rating": "NA", "id": "940f1e5d70276d8a5feaa5242d817666afa7f4b2", "job_title": "Stericycle", "place_id": "ChIJ7UpnzJjqQIYR2qG-Hcvp_YU", "address": "2525 W Bellfort St Ste 175, Houston, TX 77054, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.57188149999999, 29.9951915], "type": "Point"}, "properties": {"photos": [{"width": 4785, "height": 3190, "html_attributions": ["<a href=\"https://maps.google.com/maps/contrib/101403699241874436061/photos\">Chemistry</a>"], "photo_reference": "CoQBdwAAAGGGr-Nnxbv-P2TJJoWUQffIPXMr2wtJZQjm6pbA3Swr3X9ZmljpwSJV_hboi576Mkr9h1ue4TqSU4OekZdJQukRKEnsN7kYoa493rkpkIQ7Ow4KK09JeXgYthdxgcGB-lDHVUEtTFkGGIEc5ZEmZmTrgx7pjHFOQEQFov61uzlPEhA7-T9m4czWyFnukjaH-e3SGhSzwmRMYuo_UP8V_HDKQ1CtjZKyMQ"}], "types": ["beauty_salon", "spa", "health", "clothing_store", "store", "point_of_interest", "establishment"], "reference": "CmRSAAAAKfx6lDP0wl276myZrM2sfAi-l9UbzelF0Y5G6KEF0ojb6_TjFMqix88kz2BwFk31tsstkyu4B9GWaWvF0a5lvHCDQzORFMRYeOx7lW-ROXSN4lY704lHYvpOdQ2YFKa9EhBZgtcqei2xiHWjMmmgu9p-GhRLJh5R7aO7_NWUjAo6Rxg2CiNqhQ", "name": "Chemistry", "rating": 5, "id": "979d392b613c49fbb954ee393bff65bda5042b34", "job_title": "Rice-University", "place_id": "ChIJWxsq_4fSQIYRU9dRPmk8uIw", "address": "126 Vintage Park Blvd N, Houston, TX 77070, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.34630229999999, 29.72187359999999], "type": "Point"}, "properties": {"photos": [{"width": 4160, "height": 3120, "html_attributions": ["<a href=\"https://maps.google.com/maps/contrib/108375995272754268174/photos\">Nitish Thareja</a>"], "photo_reference": "CoQBdwAAAEmD12iearM_60k3P2APlhkWvcgUiQR0iYKkUFp92Vs7Qo7SVzv22xo6lImXDJJlX2o03tANYF24QA9tidv9PrKnwH6QIj98IHWN5NVj1u8PeMI_nuRvwxIoAJoBemqMxpZjRozuHSEDBhpMMLUpqdSGM16xf-SBIzLhoIvrepgYEhA3kogbpGMv0zAKhEwt0J1iGhSfNMel8jlT-LXbU7uPex14VQWdiA"}], "types": ["point_of_interest", "establishment"], "reference": "CmRSAAAAjOzQZMwn0WMMZ1uGmPASndzHxvvcj6T5bvUoYPWXHHh4DKjlf5q4xGEolYsLueLVrucbzXn6ECOFrcq5hJR93EKOD0wFS3_2DmuaE3xupMlztmblys5kxArXnA8fy3aZEhBmJi5Q_JbPoFlwzgTevZ8UGhSXGqbCqCDLP4NkFa9LVqXzY5f2rw", "name": "University of Houston Department of Chemistry", "rating": 5, "id": "baa83832f81135d0180e7850ce768a11f32e9df5", "job_title": "Rice-University", "place_id": "ChIJgRkjS1G-QIYRmcpaGaD6ZeY", "address": "3585 Cullen Blvd #112, Houston, TX 77004, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.4025992, 29.7198268], "type": "Point"}, "properties": {"photos": [], "types": ["point_of_interest", "establishment"], "reference": "CmRSAAAAQ_qa9BHfpUJ9cSMzgNfj2aTq1Ec3GtaiHiWQPWSyzwpeEOJ9n9KWfQC-FyLTMTxeRyXklWUqLrEBlrxVIMCg1jq-dD_Q1y8lXnpYmtJJiuei12jjjSUSU14Q4aOy8xm3EhC0wFX34mmrvfMWZgsDrcI5GhQ3OC4UtcLmqxwL70MZPIYcxfdtxg", "name": "Rice University - Department of Chemistry", "rating": 3, "id": "1553681e69a2414f5cfa7551caa2102bc22268c1", "job_title": "Rice-University", "place_id": "ChIJL8yCnHzAQIYRZRcdAPRzhYI", "address": "6100 S Main St, Houston, TX 77005, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.4166517, 29.672442], "type": "Point"}, "properties": {"photos": [], "types": ["point_of_interest", "establishment"], "reference": "CmRSAAAAYoDbEZf6N-f5xiU5BLDytH3GbfbQJHA4oCfaF2eJRfrVgWaT0YKaj1oaXEeXz1xZpTyUrJO2s-0NLtuOO35vj6PA7ZiP6YlGv1wMxp-jhs_pypPmPPX4Ol4OlBhc3a1IEhAuqwxlNxqgegwefswaGJMpGhSshlJo10ECt-NPx0Vk0MoIV_5eWw", "name": "Environmental Chemistry Inc", "rating": "NA", "id": "940f1e5d70276d8a5feaa5242d817666afa7f4b2", "job_title": "Rice-University", "place_id": "ChIJ7UpnzJjqQIYR2qG-Hcvp_YU", "address": "2525 W Bellfort St Ste 175, Houston, TX 77054, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.57188149999999, 29.9951915], "type": "Point"}, "properties": {"photos": [{"width": 4785, "height": 3190, "html_attributions": ["<a href=\"https://maps.google.com/maps/contrib/101403699241874436061/photos\">Chemistry</a>"], "photo_reference": "CoQBdwAAAK7mKIjNEpTTkfMg61px3XUsqmQxmvNbjCy-y4tM7Ywhi2k2MLxyq9bthZFydzWgoWPQi-xPkxnIqN_NtqeYaj3Y9sqMxbAImJ7IIa_-_ok4WJa2xyt__gK-IEQMXKH0kHcDejEhiPd8mVQG0lAWRdpLtC0yJhKqQFPwizRCPWbPEhAVbEz5aqBaOnThfjSV_LxpGhQ3wdPUS26MI6RE-1kxcq2AzS73gw"}], "types": ["beauty_salon", "spa", "health", "clothing_store", "store", "point_of_interest", "establishment"], "reference": "CmRSAAAA3-8L6MaKw5m4Z-7hKUz4Ul0kvWHs5arOyd59mKNErPaAG3uXjBSRk7CfkWWzAGaBRHzTgLfdN6OLSpBpse1rVhSpDwRQTsh0bKGZwjhbgFahQP7gv8hH_yR4MduQ2nPWEhB4yNXKRXvfDK-D7ANJlwUqGhR7tJHxhepq_H6oazMT9gLODR3KSQ", "name": "Chemistry", "rating": 5, "id": "979d392b613c49fbb954ee393bff65bda5042b34", "job_title": "Stolt--nielsen-Limited", "place_id": "ChIJWxsq_4fSQIYRU9dRPmk8uIw", "address": "126 Vintage Park Blvd N, Houston, TX 77070, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.34630229999999, 29.72187359999999], "type": "Point"}, "properties": {"photos": [{"width": 4160, "height": 3120, "html_attributions": ["<a href=\"https://maps.google.com/maps/contrib/108375995272754268174/photos\">Nitish Thareja</a>"], "photo_reference": "CoQBdwAAAK0mYW9eVyIIAdi3TPiDjnmm0Ly9u8oVnoxw68NjUFo_XBtaQap4Eetzr1HW0zZ39cO9YhE0ScA7zVb04eiy4t16wbevNIgbiIES99lBL2QZG9CnXsAMW4uQgRoatM8rsbtL-TU6Wz1VJRZ9IoMduV3T--bLBIt3FfrtDmWxPA9WEhBh3UEfSybg2coS1xfgz37SGhSIKbmzPm8wh-4NqERmsHq3OciXcw"}], "types": ["point_of_interest", "establishment"], "reference": "CmRSAAAAXsyWyMr329CnV_sx1ZuNCui-jDgz6_PvxQdT3JEZq1GwR4x02QjnVJ-o6EocA4pS1Wc131LY3OF1djUStYGg6rgzc_ZZ--Ffop0-gvEuiV_qUgEDopWPAN4txmyCXrDSEhBAhq1CZazjib6ZCG-eCL7iGhRy0i13PzaGUZ0mCQQN2-iHiNACfg", "name": "University of Houston Department of Chemistry", "rating": 5, "id": "baa83832f81135d0180e7850ce768a11f32e9df5", "job_title": "Stolt--nielsen-Limited", "place_id": "ChIJgRkjS1G-QIYRmcpaGaD6ZeY", "address": "3585 Cullen Blvd #112, Houston, TX 77004, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.4025992, 29.7198268], "type": "Point"}, "properties": {"photos": [], "types": ["point_of_interest", "establishment"], "reference": "CmRSAAAAdL1hLwnatdoBd5ImwBcqmQRWGuYprhOC7a6zCZ8DUitam1aISrMnGGcyY_5d_k2ll1JB2oStVTx9Hugffy5BGLJqPEw0YlbFhPztVvVEAyhdh8Lxj9T5_oai9FJfS91rEhBcSz0vBM78DrIMP_7_qSOYGhR51FI7biiT_gbiCFGaDmlQrv7m7A", "name": "Rice University - Department of Chemistry", "rating": 3, "id": "1553681e69a2414f5cfa7551caa2102bc22268c1", "job_title": "Stolt--nielsen-Limited", "place_id": "ChIJL8yCnHzAQIYRZRcdAPRzhYI", "address": "6100 S Main St, Houston, TX 77005, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.4166517, 29.672442], "type": "Point"}, "properties": {"photos": [], "types": ["point_of_interest", "establishment"], "reference": "CmRSAAAAEEn1kfNMDmoYMJRKQcCbxFhUuDqIn49tUim7_oMjMQP0T1028s1UWOYlfH04tL2jo9wsgXQPVonQLIMlIH8nzC7ZmxGop-Imffbyubyus5wu7z0Bw0GY0fJWHsW8O1-QEhASCIw7FYZMU_lnT2frtcwnGhTG_Nv8DxvQ3p-uwj_tu2iDgEK_Ng", "name": "Environmental Chemistry Inc", "rating": "NA", "id": "940f1e5d70276d8a5feaa5242d817666afa7f4b2", "job_title": "Stolt--nielsen-Limited", "place_id": "ChIJ7UpnzJjqQIYR2qG-Hcvp_YU", "address": "2525 W Bellfort St Ste 175, Houston, TX 77054, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.57188149999999, 29.9951915], "type": "Point"}, "properties": {"photos": [{"width": 4785, "height": 3190, "html_attributions": ["<a href=\"https://maps.google.com/maps/contrib/101403699241874436061/photos\">Chemistry</a>"], "photo_reference": "CoQBdwAAAAVKRPuig1BpgL3xLKlkodZg5Sz_nDI92RVwSDLTpj488JyObc4bZeJDW6mX_Znts7_FBKLZo6Slb72cSjg3pI3J7IfhMQHQ1wvx9zAIuGcE0qkt0LrO4SVHnRMH_dSzSzPy8_yB1SpZcu03J17WFRRamlAx2tTQVXKBacf9zDUmEhB--Okf0aGIIo5N5ybLq3iPGhT4pBwWEYMoQ0YzCdsrp2lfAi1jQA"}], "types": ["beauty_salon", "spa", "health", "clothing_store", "store", "point_of_interest", "establishment"], "reference": "CmRSAAAA-cvqzofOShCS7AxGulSTKFmhQI0XiNBAldHqauu_UDLLFv4sT8mL06FQTtalmNtQ5Isb6uR6NbBJqrQK_aJQqykLYdXzdKX_VhleYoTIxwba7x8kn4Mdf6YPWsWAD5YiEhDmsNr-fraSLArnGZI6QNWMGhRFnUqqPpMlbSfJ49rrzHSWfoIWaw", "name": "Chemistry", "rating": 5, "id": "979d392b613c49fbb954ee393bff65bda5042b34", "job_title": "Staffing-the-Universe", "place_id": "ChIJWxsq_4fSQIYRU9dRPmk8uIw", "address": "126 Vintage Park Blvd N, Houston, TX 77070, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.34630229999999, 29.72187359999999], "type": "Point"}, "properties": {"photos": [{"width": 4160, "height": 3120, "html_attributions": ["<a href=\"https://maps.google.com/maps/contrib/108375995272754268174/photos\">Nitish Thareja</a>"], "photo_reference": "CoQBdwAAAFVDk78_4UJVcOPlx95Oluk6X5LyKW897NHO74kpBsQIBsxNpkbtFbY7-9mnSOfXUnYqQrs0EQyr0po-4nlN3cEcLFi3cnwBfdY2XnVengMtb1PciBwPsqoRm9cxKfqI2OJIgw0GFdlGtU0V-6Vr9mDptlBSy0-lPYovoWpXsgyPEhDWJ2WSWzfMeylZUxGLqJF_GhQULI74gcglUFZsZCuC_zkUJMFXzQ"}], "types": ["point_of_interest", "establishment"], "reference": "CmRSAAAArZoDI7J-EEJyx83qNT-688IUoK9bKQ_bGjsM_XzFxNAaUJ8QIzdGkpXYffyi6Zfl56MvI_I0n9Bi4XTWmu1OD3tmTpIaCLFbrhxrv9NK4uVE580Zv9DSdblkoAEc4gBJEhDyWThWk5NkcoS29TYGZo-mGhTK5Ci7SNG1KuNjAtx2Lma7Ecl2Dg", "name": "University of Houston Department of Chemistry", "rating": 5, "id": "baa83832f81135d0180e7850ce768a11f32e9df5", "job_title": "Staffing-the-Universe", "place_id": "ChIJgRkjS1G-QIYRmcpaGaD6ZeY", "address": "3585 Cullen Blvd #112, Houston, TX 77004, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.4025992, 29.7198268], "type": "Point"}, "properties": {"photos": [], "types": ["point_of_interest", "establishment"], "reference": "CmRSAAAAGzJXqrvWXBjAj04VwrDGxq4OXzwMqfPgxjpbePC8SueuQ448G2VMz-ECwJ0DqV4F_atUaLQAeQdoaeddvUv4vq7A2KxHosPD962ipryyfCoxYJp3vuYOxXNXnuXr5_doEhDa4TNTL6PfFMfGgbl33ymGGhSw3CUo5ii7LePx2IfpaEuIjvReTA", "name": "Rice University - Department of Chemistry", "rating": 3, "id": "1553681e69a2414f5cfa7551caa2102bc22268c1", "job_title": "Staffing-the-Universe", "place_id": "ChIJL8yCnHzAQIYRZRcdAPRzhYI", "address": "6100 S Main St, Houston, TX 77005, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.4166517, 29.672442], "type": "Point"}, "properties": {"photos": [], "types": ["point_of_interest", "establishment"], "reference": "CmRSAAAAN9xFeBpEUK1CWqO5PMuovag2zbiygSSIZ7sLxwDLUx5uVR4hsihnrFSuEVYf0X9cQJr_CpnOZF6vgTHcCsRuzP-NPXVm9pXeiWOgXBhMX60sabw1m3ErK9Tu4W3hs4N4EhCb2Y9VBDJIRTPY2jo-taWTGhRa9Gtq76VUAZg2206XbCZ9bk9r7w", "name": "Environmental Chemistry Inc", "rating": "NA", "id": "940f1e5d70276d8a5feaa5242d817666afa7f4b2", "job_title": "Staffing-the-Universe", "place_id": "ChIJ7UpnzJjqQIYR2qG-Hcvp_YU", "address": "2525 W Bellfort St Ste 175, Houston, TX 77054, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.57188149999999, 29.9951915], "type": "Point"}, "properties": {"photos": [{"width": 4785, "height": 3190, "html_attributions": ["<a href=\"https://maps.google.com/maps/contrib/101403699241874436061/photos\">Chemistry</a>"], "photo_reference": "CoQBdwAAAMDYU8TnN5KTYJn1c3QvX3n8ZFF9djs3FbdEHAgVFG2ywKxqKhT73j5YK9_Bj67W_zzjs4kE1DEb5OdO-eC5k09TPjVxfj_hnAXgYN1Z9g-xd6L3VUOa_vg2do8GPTFMKDTA1EJud_VHOk_mNFsCL-ph9PAhkvzpBAQ4_62gecWUEhB-gUF3hIiebMIoQ0buMAALGhQovscQGMdWqtEbx0diO70KDJ1IMg"}], "types": ["beauty_salon", "spa", "health", "clothing_store", "store", "point_of_interest", "establishment"], "reference": "CmRSAAAAAPT5EFpxp4-DEg4PLJwnexMCkw6-Xcy4j2A1S0rkwNoY_ktYBWScLzTDStX4VWCP751Q6DpdKbPOTboZm8dn0ehYsIPh0kyqfdbekcAO73aN_nEG_EWDWTOpQwCIB-LNEhCUONDr9zouh4DFy0ofduZ3GhSYAKHuiuyRbgANxx_I3ySEusOTtw", "name": "Chemistry", "rating": 5, "id": "979d392b613c49fbb954ee393bff65bda5042b34", "job_title": "Assure-Oilfield-Testing,-Inc.-1", "place_id": "ChIJWxsq_4fSQIYRU9dRPmk8uIw", "address": "126 Vintage Park Blvd N, Houston, TX 77070, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.34630229999999, 29.72187359999999], "type": "Point"}, "properties": {"photos": [{"width": 4160, "height": 3120, "html_attributions": ["<a href=\"https://maps.google.com/maps/contrib/108375995272754268174/photos\">Nitish Thareja</a>"], "photo_reference": "CoQBdwAAAF-QkY7819eeVH6mn8OyYGhVfyzC712otMIIc0zVfvOZgcXKL8ATVwPNtekKqWwT-OkpJ3zmot04wMzL8E-cnvpWpfAra8hXQno858KAxVkVMAj3P8ABaHwj-faSWmoesx1M9L96QRq246qyd653DzzpF5WH4yasdRKMgblWHgw3EhAvT8zRE46uPFMZOMyU3T2CGhSMJmA8dodT-WOuJupPbV8jrJoCuw"}], "types": ["point_of_interest", "establishment"], "reference": "CmRSAAAAlx9Hvka3bAZT2c_bD3vs3HbDLPvp4VeQsgBpiq6kgZW72KZU_o_vey4DLL1t8kHquN1vn4k1uHIPqyhnprWErdcbqYRdhJ7NM7GU1gUDhvAyGQip2731GSXIw1Hcjcz_EhDQkZKHA_l1SPfkZRprDDbCGhQGWnlt3lK9XThNuLs70fD5EmPaEg", "name": "University of Houston Department of Chemistry", "rating": 5, "id": "baa83832f81135d0180e7850ce768a11f32e9df5", "job_title": "Assure-Oilfield-Testing,-Inc.-1", "place_id": "ChIJgRkjS1G-QIYRmcpaGaD6ZeY", "address": "3585 Cullen Blvd #112, Houston, TX 77004, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.4025992, 29.7198268], "type": "Point"}, "properties": {"photos": [], "types": ["point_of_interest", "establishment"], "reference": "CmRSAAAAAhyCcy-jEd1VwM7DM58Al44p8U2TbDMcOecIoy4e5ckSBiPFUp3b-YB9gW4LQATzQpOHO_Aw0-2hYQ0JmgmLwZj6UqXArhE0IKSsiKM7p559Yku50HPOASakD0vFuO39EhCRDIiBhb2Qc9JMhUqpNxzxGhSwyrbZfWO_ZB8EsjTVZab4JtFUsg", "name": "Rice University - Department of Chemistry", "rating": 3, "id": "1553681e69a2414f5cfa7551caa2102bc22268c1", "job_title": "Assure-Oilfield-Testing,-Inc.-1", "place_id": "ChIJL8yCnHzAQIYRZRcdAPRzhYI", "address": "6100 S Main St, Houston, TX 77005, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.4166517, 29.672442], "type": "Point"}, "properties": {"photos": [], "types": ["point_of_interest", "establishment"], "reference": "CmRSAAAArmW2qd6TCZz3Uq6vpIBny_rPdYd5onNE9QsxtsCAjSD7X-ITkhZehTfhxX1U73R9I-H47VEqSjIBXepfpePtowW7E1UjRkKQaYZW5f9qyDfuD7NbhZDn_JO0u2zDDYlOEhCs_MX-Vr1o-cfvu3Nwu1ZJGhSPytv7uzCcDfKwNC_eJx1X7QnfGA", "name": "Environmental Chemistry Inc", "rating": "NA", "id": "940f1e5d70276d8a5feaa5242d817666afa7f4b2", "job_title": "Assure-Oilfield-Testing,-Inc.-1", "place_id": "ChIJ7UpnzJjqQIYR2qG-Hcvp_YU", "address": "2525 W Bellfort St Ste 175, Houston, TX 77054, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.57188149999999, 29.9951915], "type": "Point"}, "properties": {"photos": [{"width": 4785, "height": 3190, "html_attributions": ["<a href=\"https://maps.google.com/maps/contrib/101403699241874436061/photos\">Chemistry</a>"], "photo_reference": "CoQBdwAAAAA_6K3q_yfZ2sra5khXT9XJKXWx0XV7J26jWykAVxFau7vnse_2CT0Ht_f5FBl_-fQJfzdRuemhebdf2lnDuBIGlPRMeO8N0c7gAgf5wBi_Ew8bTth6ARVpOox1dLM128pVLh_Z2cXLwFg5ZAHSd8_Dwlj4Jvtag6lzlbY9zShIEhBY2xycXOkGaesL6k0ukt0QGhQV3zZ6-uGcA3jQJp_XsWYkhswLfg"}], "types": ["beauty_salon", "spa", "health", "clothing_store", "store", "point_of_interest", "establishment"], "reference": "CmRSAAAA2A2Nwptjyn3SZyXAHpj0jG9KVzP8p3KjUep8s_HwqcT9CYwYq88gpWIAkCtHMnAveD9mqB2PYdJuLIgo_FUXFaImf7J8WFASWoPn6yNnHR88327hKl6SDOeJHm6IUI91EhCgUdcnFzxDGVFwnNJGHzHFGhRqVIR3zMisnGgjvZ-G_IrOV5F58Q", "name": "Chemistry", "rating": 5, "id": "979d392b613c49fbb954ee393bff65bda5042b34", "job_title": "Halliburton", "place_id": "ChIJWxsq_4fSQIYRU9dRPmk8uIw", "address": "126 Vintage Park Blvd N, Houston, TX 77070, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.34630229999999, 29.72187359999999], "type": "Point"}, "properties": {"photos": [{"width": 4160, "height": 3120, "html_attributions": ["<a href=\"https://maps.google.com/maps/contrib/108375995272754268174/photos\">Nitish Thareja</a>"], "photo_reference": "CoQBdwAAADNK5O-OEy1ZhCWWJDykD6LUHh66d4OZHbn76zL60LFZk-IyJUFmI_SwH5LXvMfDJWpCZy8qi35-wU2zSITn_3EjQfjI_GQvXCF0q5G2O454i4Q07-l9zMXd2N0Z4dtqlb6xYLfO69cTUi5nERsdTCrYGkiT_Xz4mp_etQqlirZlEhBrYikdhWesrErPusFpPtcYGhSOVeHTvlP7VAeR3yRGu7PjvIzciw"}], "types": ["point_of_interest", "establishment"], "reference": "CmRSAAAAFaG7YL1dl7l0esjCtmeTXeiswN3cs0WpLwcsTt0Lop8Z4Yu0WxxqpRH9ws_cNjA8zJbkcbYk_4OAMX1nDZ7zwaH5qJf6U5gYaGHHVOMHez_W6piOkCbhAHWoH2h_Q8EEEhDHDdMTJHtZjxSvLYGp6Dw1GhS9UKk0BeP11FlP735BzgZGKQoE7w", "name": "University of Houston Department of Chemistry", "rating": 5, "id": "baa83832f81135d0180e7850ce768a11f32e9df5", "job_title": "Halliburton", "place_id": "ChIJgRkjS1G-QIYRmcpaGaD6ZeY", "address": "3585 Cullen Blvd #112, Houston, TX 77004, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.4025992, 29.7198268], "type": "Point"}, "properties": {"photos": [], "types": ["point_of_interest", "establishment"], "reference": "CmRSAAAA4cNwWhOXCsQi0LvvpAfGa2vtcgIWm2-kGdK5FWOVSCIsB0gsFeWhYy9NwO2yyBC_FO4ifY615QhEYDkYy0Ij4S7mCOhzvheeIhiHvDP2ljgkRa4nA7V4pYZjP0RwIGFoEhBcZtyxevzpurIIyoDbPPg_GhTMFWgSQ7SqGM5IMvust0N2v_mgUA", "name": "Rice University - Department of Chemistry", "rating": 3, "id": "1553681e69a2414f5cfa7551caa2102bc22268c1", "job_title": "Halliburton", "place_id": "ChIJL8yCnHzAQIYRZRcdAPRzhYI", "address": "6100 S Main St, Houston, TX 77005, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.4166517, 29.672442], "type": "Point"}, "properties": {"photos": [], "types": ["point_of_interest", "establishment"], "reference": "CmRSAAAAczyAdHcYIi4zS7B_elTCyDsq4P6_is1F-HzsaI_WQPiWjnPqjVUUxLmUIqzdCdl4mGJg-Kj23KSoFYHjwK7rCpj-hMs1MBTDNasjRwc05GKVceGRd3b9fw3byHmM5MfnEhAoGNnaKT2CRoFR6LqjhVPPGhRJNxBs1ELF1qG4rbX5zOx2NJxwbw", "name": "Environmental Chemistry Inc", "rating": "NA", "id": "940f1e5d70276d8a5feaa5242d817666afa7f4b2", "job_title": "Halliburton", "place_id": "ChIJ7UpnzJjqQIYR2qG-Hcvp_YU", "address": "2525 W Bellfort St Ste 175, Houston, TX 77054, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.57188149999999, 29.9951915], "type": "Point"}, "properties": {"photos": [{"width": 4785, "height": 3190, "html_attributions": ["<a href=\"https://maps.google.com/maps/contrib/101403699241874436061/photos\">Chemistry</a>"], "photo_reference": "CoQBdwAAAJoFbM5eNly8F9WiJ7yAR9j9kKXr472XLR2qo69idcipU-YPjbzu4sN8cSUYR8OhyarzzJ0dmG2USb2Etsj8z5Z8F0KccAdixkoKepA0M-MBNhkxE69cjJeOmV02CGlR9idS-BNEtM6oMDWSXMFQJcaIElatlWQRNTdFNyPleVqVEhAuIEaJvOUu6slLuyr1nzxjGhThGgi7GCYqps8w2K2A2AONUQEYPA"}], "types": ["beauty_salon", "spa", "health", "clothing_store", "store", "point_of_interest", "establishment"], "reference": "CmRSAAAAAmXMwjnhUaSgxjjmlVIp1WM_5czRSOQxlu53rNn_LscSaWAhQHzYStwHDC9HQKmnXYzPIoDch6nFi5te6M9b3TaQa-ooopvdsagDk9078_Ey_PD2bIsjoTDu1vrAsO60EhBM3w4glfPOHsglH5-9isubGhSrplO5KQC_tsnEby7af0_aeeVsLg", "name": "Chemistry", "rating": 5, "id": "979d392b613c49fbb954ee393bff65bda5042b34", "job_title": "Labtopia-1", "place_id": "ChIJWxsq_4fSQIYRU9dRPmk8uIw", "address": "126 Vintage Park Blvd N, Houston, TX 77070, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.34630229999999, 29.72187359999999], "type": "Point"}, "properties": {"photos": [{"width": 4160, "height": 3120, "html_attributions": ["<a href=\"https://maps.google.com/maps/contrib/108375995272754268174/photos\">Nitish Thareja</a>"], "photo_reference": "CoQBdwAAADITgK_LjQLzPkpb4b5b-L84XVjn4H9VV-Eqnk4IdvqPH4ZV6njAAOQVXu1AwB1nEO4ZOeuC4I-D7w8zGwJfbk8sqbZ3eM4XHvTktisYlYxstqlu3n5jicsrCr2zBdHKvMNJ8BH06EAcZdCb2fE3X7L7bOP8kMSN1m3DeQM5mQa9EhACCGHFfgP7ijR7j7h1OkamGhRr7tLmPdYszGDZOED27pjGKhi5zg"}], "types": ["point_of_interest", "establishment"], "reference": "CmRSAAAATSrHBikQ-DEufCKfBIOCsVKcqXPEziVhBhoxNvpyviv64fCR1bqSpbXsgOBoYa7AHyGU762X7EBc_fk7Nx2JpaIN7ciEmmKIFMtoUoi0AkaCYAsXZgYY7GVGOidJezcvEhAwZyr-OAHVBPgTsa9qQjXxGhQC0p10j7KakAv8N28UIoVo7lrcQg", "name": "University of Houston Department of Chemistry", "rating": 5, "id": "baa83832f81135d0180e7850ce768a11f32e9df5", "job_title": "Labtopia-1", "place_id": "ChIJgRkjS1G-QIYRmcpaGaD6ZeY", "address": "3585 Cullen Blvd #112, Houston, TX 77004, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.4025992, 29.7198268], "type": "Point"}, "properties": {"photos": [], "types": ["point_of_interest", "establishment"], "reference": "CmRSAAAA_itWnuMVs6edGi50mNW5igGucAKeK0XttaCP6Ys97KuoyfmwqsoDnLIf_8-K4SFL7oaWxiWkULj0U9_eQ1ds-dEV0W2woP9AejTu5ncHFkWwm_441mDN5O7CNG54lMhvEhD992HSpcD34sUDKAX_yE-LGhRitNz5U3uTjf1AZ6cTRfsrASkO0w", "name": "Rice University - Department of Chemistry", "rating": 3, "id": "1553681e69a2414f5cfa7551caa2102bc22268c1", "job_title": "Labtopia-1", "place_id": "ChIJL8yCnHzAQIYRZRcdAPRzhYI", "address": "6100 S Main St, Houston, TX 77005, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.4166517, 29.672442], "type": "Point"}, "properties": {"photos": [], "types": ["point_of_interest", "establishment"], "reference": "CmRSAAAAQTrydy4K4CJJIBM-VLPA_cgbgb2r3-OQBnkz4UhqhKWVH9vF7OGT8Wq1xcmfQ1C37nFBit9JiLFHGUDUcXGpxG879T7T4UiYzO1gAHUny5dJ-EysKWV3n0RpkwInwGQbEhD21omh3Z_XcWIEihwxgCL_GhSXrWA2LYWVWGftfNhUthHnx2Jqxw", "name": "Environmental Chemistry Inc", "rating": "NA", "id": "940f1e5d70276d8a5feaa5242d817666afa7f4b2", "job_title": "Labtopia-1", "place_id": "ChIJ7UpnzJjqQIYR2qG-Hcvp_YU", "address": "2525 W Bellfort St Ste 175, Houston, TX 77054, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.57188149999999, 29.9951915], "type": "Point"}, "properties": {"photos": [{"width": 4785, "height": 3190, "html_attributions": ["<a href=\"https://maps.google.com/maps/contrib/101403699241874436061/photos\">Chemistry</a>"], "photo_reference": "CoQBdwAAAMH18ln03FhaLitNRr8dJSV84pDnj8L3KwyxQkCc8MIIBcDFSjBE3s7ijcooTRVbbvly-tzBysE94J5XRY7VBU8i8Bjq61jt4F-Cnu6XSVruh1180cM1FY_dHbUVqfAyNert6MieI0UTL5D_zHuWEW7EghPzCWxEW5R78yKjRMTrEhAbukm5x-vPKugbuXK1UT55GhRZe_farivmkMlhrz1AIkW2kjQgeA"}], "types": ["beauty_salon", "spa", "health", "clothing_store", "store", "point_of_interest", "establishment"], "reference": "CmRSAAAAl_QPuYdIoURTwT453PT4rdZ3ZziyhlfcstdlHHnQ10scBN3lfM_EugsrhTQBQ6QF9FSUTnV-knp9Gc75kjXjfCHvs_4jaX3QUxY1lSUWxzAMbz7yRdX61E8FRS0IGKdIEhCVNvHVaA6I-7Lesgan_rpOGhQ_vXcPQdhb2dXVCSjzgSVxFsHYGg", "name": "Chemistry", "rating": 5, "id": "979d392b613c49fbb954ee393bff65bda5042b34", "job_title": "Nes-Global-Talent", "place_id": "ChIJWxsq_4fSQIYRU9dRPmk8uIw", "address": "126 Vintage Park Blvd N, Houston, TX 77070, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.34630229999999, 29.72187359999999], "type": "Point"}, "properties": {"photos": [{"width": 4160, "height": 3120, "html_attributions": ["<a href=\"https://maps.google.com/maps/contrib/108375995272754268174/photos\">Nitish Thareja</a>"], "photo_reference": "CoQBdwAAACXnkdkgIeS6h896BGyGw3ad8-L3TvZvzCkWG2f7h8IZh5YGnRQ2ClqwvuTtEkoTHWnLAufATawedUPgCHafNEB_gPxDnPi4Rq3BayIUUtbmvKafGdmgnbDAFvs1UxrkOxBPmKCc08mikib_s3Zn-n93JGQ2nWfu8rg4vohsleT3EhCFe-lyJq3Uji8KrTGsZwVhGhQ6yL7R9GC3oLf1qdl44YK5Cv-8GA"}], "types": ["point_of_interest", "establishment"], "reference": "CmRSAAAAJ4k3WSMNDkcHm3FIa082bewXYXxx1sx5dQTptkLnfmrh0IPhdJwUAcLM_dVB8tivTq3Qs2X0LcGNyggAlCki3kCvkSEeSnOrMASPbbjJTP4CFNSjPsYVPr1e_jzNHvaVEhCwKVPB9KGfdqD8sfPiX2jJGhSFPwvyvasdVpCSx8OUos8Ipdm7YA", "name": "University of Houston Department of Chemistry", "rating": 5, "id": "baa83832f81135d0180e7850ce768a11f32e9df5", "job_title": "Nes-Global-Talent", "place_id": "ChIJgRkjS1G-QIYRmcpaGaD6ZeY", "address": "3585 Cullen Blvd #112, Houston, TX 77004, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.4025992, 29.7198268], "type": "Point"}, "properties": {"photos": [], "types": ["point_of_interest", "establishment"], "reference": "CmRSAAAANbiJ63r4fBhfx3LypTT-rzKQp_NRaRBL_HcyZwqePvKxxOOfBdTKySpcLDVi_1gP8DbZTP0_qo2ycWVTFxswq8BPL0qPu4oN0saFrGmaiFyPzpCA3nivwYiXWiKLl7JzEhCIcU-GkVACMSXBjfbwQ12pGhTRPX6x1WvV96lWMcqCoypt8cXQuQ", "name": "Rice University - Department of Chemistry", "rating": 3, "id": "1553681e69a2414f5cfa7551caa2102bc22268c1", "job_title": "Nes-Global-Talent", "place_id": "ChIJL8yCnHzAQIYRZRcdAPRzhYI", "address": "6100 S Main St, Houston, TX 77005, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.4166517, 29.672442], "type": "Point"}, "properties": {"photos": [], "types": ["point_of_interest", "establishment"], "reference": "CmRSAAAAQ4-suqxBpKY8v2R7zeFpFydA-PBsgmPHHkxDLMgOoljbOdTB7NhBTqqCy80zTn-3nZHXp4xlhmaFeRBedMfpuNGVbrOCIInlPSzeTtyG6v1aTIpdB2P_-GGlBVXhu4_fEhCcO4VA7JAHCkYme4Qs1fTrGhR484DEa3GoKj0_ZtshjfEW0HD1Dg", "name": "Environmental Chemistry Inc", "rating": "NA", "id": "940f1e5d70276d8a5feaa5242d817666afa7f4b2", "job_title": "Nes-Global-Talent", "place_id": "ChIJ7UpnzJjqQIYR2qG-Hcvp_YU", "address": "2525 W Bellfort St Ste 175, Houston, TX 77054, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.57188149999999, 29.9951915], "type": "Point"}, "properties": {"photos": [{"width": 4785, "height": 3190, "html_attributions": ["<a href=\"https://maps.google.com/maps/contrib/101403699241874436061/photos\">Chemistry</a>"], "photo_reference": "CoQBdwAAADCtHMt8pcGVbIiasaza0May7W3C6h8jqYw487_mG8S_KSq7tfbkUhDPsv2NdTxmCRkeWOdMyMAoyPnPb69mXA1GUmsuF5qDNzTLHZl361xulX9eQyJkaW21cFWTmrBQN0YOxAoq0FGnoZ2GLBTTpunzaDlGwsONlS6j4kkR3feXEhDHmhHEcP3nFyqYjnKZQPMTGhRlVZLOafOvtsXJohdGvYAxDYfNbA"}], "types": ["beauty_salon", "spa", "health", "clothing_store", "store", "point_of_interest", "establishment"], "reference": "CmRSAAAA-d4kv78rGtl6XGggixAU9bju_8c3K_AUttK8gBhhZssNGJ7n3_-O0PfBniSyJHykL8F5YEgGmzrtyFeeatFqrcjgU4n4olmeAlJcJx_4GkoGKxqLEHn52kJub5OWb-rNEhBgFIidZTEIMWk7QFQnXokjGhRl00-e01vsbHDSgQvdNxWKEWFLbg", "name": "Chemistry", "rating": 5, "id": "979d392b613c49fbb954ee393bff65bda5042b34", "job_title": "Doble-Engineering", "place_id": "ChIJWxsq_4fSQIYRU9dRPmk8uIw", "address": "126 Vintage Park Blvd N, Houston, TX 77070, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.34630229999999, 29.72187359999999], "type": "Point"}, "properties": {"photos": [{"width": 4160, "height": 3120, "html_attributions": ["<a href=\"https://maps.google.com/maps/contrib/108375995272754268174/photos\">Nitish Thareja</a>"], "photo_reference": "CoQBdwAAANGEjtSDhENt_d1RrX4wpOMZVRJVHcfSHBosT2qntkJeyF_dRld0mDCmDMMLqfG8gWPGHPvfA4xny2IoqupV_vbtedonKAJh2uPywHxQcJ4n2waw2bAL45dvxiUT2ous-Lw0K43upJbNSAFFawyJjHtv7B0jaaE5VRPsMX8IpVA-EhA25A3hAvevg9jHk5JKRVojGhQx4-WF7mdAE9tx20VNG2-hn5ZSSA"}], "types": ["point_of_interest", "establishment"], "reference": "CmRSAAAAPby5zKC5yr8d5V9eDieKxgNeyj2ZbbkNLxP2uxy23bG1rMJ9Awj_7YndxDcDp8n8tSQOdxbCgFh2FwA0jVmDGB0VOjoFKRKPlVxfw9K3LSEitKOMfrtyD1yq3j4J66OeEhD-okivjipC7M1CTK2A4moQGhTW-sD-CnwbJUyQjB17amAfCHIvFQ", "name": "University of Houston Department of Chemistry", "rating": 5, "id": "baa83832f81135d0180e7850ce768a11f32e9df5", "job_title": "Doble-Engineering", "place_id": "ChIJgRkjS1G-QIYRmcpaGaD6ZeY", "address": "3585 Cullen Blvd #112, Houston, TX 77004, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.4025992, 29.7198268], "type": "Point"}, "properties": {"photos": [], "types": ["point_of_interest", "establishment"], "reference": "CmRSAAAAQwImesrQ5-I_FeSYdQV28l9QXEtvV4DwW1WKMcOYYbYCVf6FFehRuN5lCPn2W3zap8pQcBDSOdKgemuaXdKcErvDjifmwlnJN2dnbBHZYyrRNJZVyET-Cgpq0DlCa_i9EhBVgw7q-4g--8FW4qfqzPS-GhQa1lb56V6FVNt0T4lmb33nYrKzZg", "name": "Rice University - Department of Chemistry", "rating": 3, "id": "1553681e69a2414f5cfa7551caa2102bc22268c1", "job_title": "Doble-Engineering", "place_id": "ChIJL8yCnHzAQIYRZRcdAPRzhYI", "address": "6100 S Main St, Houston, TX 77005, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.4166517, 29.672442], "type": "Point"}, "properties": {"photos": [], "types": ["point_of_interest", "establishment"], "reference": "CmRSAAAAL4ch9lCbCW6S4NFNxsivAXCZAkEqdmzoFYG_TYYC45xjNQjdDlOoxc0lqIWUstBnwge0pGlclbEFSXpBqGE152WrtbYIdyQjI7Xb0KksAYGDagE8W3dqATRzTSo2_NjtEhA3V3OUp1s2RbLRjVHCfH_mGhQVn4oOlC_H4MV8esb6_KeH0ySg_g", "name": "Environmental Chemistry Inc", "rating": "NA", "id": "940f1e5d70276d8a5feaa5242d817666afa7f4b2", "job_title": "Doble-Engineering", "place_id": "ChIJ7UpnzJjqQIYR2qG-Hcvp_YU", "address": "2525 W Bellfort St Ste 175, Houston, TX 77054, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.57188149999999, 29.9951915], "type": "Point"}, "properties": {"photos": [{"width": 4785, "height": 3190, "html_attributions": ["<a href=\"https://maps.google.com/maps/contrib/101403699241874436061/photos\">Chemistry</a>"], "photo_reference": "CoQBdwAAACmhk7orBuhe6KCBpwYecna5of-7-YKvOMkE52vzOnYuU5QbWwBvAiCid_c6Q9pLbeB4TujMqumuZLrG9499BHH1HSISuojBxuak8ZR0zuNzQFL7V3GMzWnsIH8tsgY0bl3TS2p_z1iv2vXdIsINrtpv7Tdx06oiOaRY7TBfIHDnEhCMLNjKHa_ElBSpsnYSlQQfGhTFEjSoUjtJl0w0e356cxbSRTrXGA"}], "types": ["beauty_salon", "spa", "health", "clothing_store", "store", "point_of_interest", "establishment"], "reference": "CmRSAAAAx8qn8ParvNsP9eOClAmOC1hkMJSuQnfmxtdEWffrKNWGAf_A90ztcg93SsSVQ2dcPKC5NDYbGfAZTR0-_lq3hSjgztmjtFabjglsA325XQ51sqDWL5ZMecEOJc-Hv18FEhCjw9kYVAIGYyF2cgeIYJrIGhS9dK9kDh5pDVePgRKqD1_-LsMS_A", "name": "Chemistry", "rating": 5, "id": "979d392b613c49fbb954ee393bff65bda5042b34", "job_title": "Kelly-Services", "place_id": "ChIJWxsq_4fSQIYRU9dRPmk8uIw", "address": "126 Vintage Park Blvd N, Houston, TX 77070, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.34630229999999, 29.72187359999999], "type": "Point"}, "properties": {"photos": [{"width": 4160, "height": 3120, "html_attributions": ["<a href=\"https://maps.google.com/maps/contrib/108375995272754268174/photos\">Nitish Thareja</a>"], "photo_reference": "CoQBdwAAAHPNpNVR5F1vRBTttWcgisPMZb2ceIg88UuRFBRCC6OJa_-MoBlZV23jnKN-_EELVA3rGqsng3jbfW7oC6MDTHNEidxtc5JRSBZECwGsXOrpGATuB9vDwD7yO-1GK2RxbWnWa6eRPp14pTLX7fzGBSGs-oaMU_4XjgYTVO07nnR6EhB8HLQYIJfxqmaURb4abb0NGhRZ8R-uUucReZXRaPWFF2tqnR1UDQ"}], "types": ["point_of_interest", "establishment"], "reference": "CmRSAAAA34eJcb2Jenj7GX7wrdWIbsAXYFpOnp7Lz3Y1Md-Ko3Ek73bwQfRFCogy0X0k4TJCIeu-CfMLlitmzXhRB4Us8JmKmd9U7daXXDlXt3-_nJ5J70E7yRk7SBym6Y_gmpxaEhB7Xr5AZWO6WgVsyB49YvaEGhTUGwmfBfqhf7t2ocph-L1bzkGLtA", "name": "University of Houston Department of Chemistry", "rating": 5, "id": "baa83832f81135d0180e7850ce768a11f32e9df5", "job_title": "Kelly-Services", "place_id": "ChIJgRkjS1G-QIYRmcpaGaD6ZeY", "address": "3585 Cullen Blvd #112, Houston, TX 77004, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.4025992, 29.7198268], "type": "Point"}, "properties": {"photos": [], "types": ["point_of_interest", "establishment"], "reference": "CmRSAAAAJO1o2C35_sQHRXNhQ0e6NHSZyvE2JdXzCtDVNU-Ua1ILkbyrnFmg05bYyUjTPQ9p1CoFb_krvw5dR4QyTmM1Odi0y6ZunYOAiCaF0hrYnOMqwEcVumGjBH3L2GH9ECSoEhA7sljyPjJbGnbPhROAAhtdGhR06ZeWlZ49cXhsHe8DZK1Q1zvqgQ", "name": "Rice University - Department of Chemistry", "rating": 3, "id": "1553681e69a2414f5cfa7551caa2102bc22268c1", "job_title": "Kelly-Services", "place_id": "ChIJL8yCnHzAQIYRZRcdAPRzhYI", "address": "6100 S Main St, Houston, TX 77005, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.4166517, 29.672442], "type": "Point"}, "properties": {"photos": [], "types": ["point_of_interest", "establishment"], "reference": "CmRSAAAATdCZTFFB6GZeNrRA3nCGNKLapQYm9B193__dT7JWCZ0MYgr9AXQ4CJ668af_DcL9FZCcosjsTRV2xg2z5qfAiVbNnG66ZzlZJLXJFvcKEjZQO7dGuqm2jgDhhdnwCCO6EhCyu5h11lpMmRfvD3scCgXnGhTWX2cVsiqceR0t8aC7YHrh7zTUoQ", "name": "Environmental Chemistry Inc", "rating": "NA", "id": "940f1e5d70276d8a5feaa5242d817666afa7f4b2", "job_title": "Kelly-Services", "place_id": "ChIJ7UpnzJjqQIYR2qG-Hcvp_YU", "address": "2525 W Bellfort St Ste 175, Houston, TX 77054, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.57188149999999, 29.9951915], "type": "Point"}, "properties": {"photos": [{"width": 4785, "height": 3190, "html_attributions": ["<a href=\"https://maps.google.com/maps/contrib/101403699241874436061/photos\">Chemistry</a>"], "photo_reference": "CoQBdwAAALxujBI9ibbKDgDNNtTn5pWkws5O-t26Z-6InDv-3BKo7RYEarroCmOQGful0U66Ma74a3AjZn5DcDuPnoPvj3-JdJhP_DRD09RJ9t1MBEqynpKxJxRmd7kUHz9sqOFgjtjBzFIgQ9_xASMai3bJ9LHUbhSnJVLiBbqtSw_zwmWeEhCfryNs4K58806Rgu34GZUfGhTFCYyK7CUxHXtuikC0_iY2UKvnhA"}], "types": ["beauty_salon", "spa", "health", "clothing_store", "store", "point_of_interest", "establishment"], "reference": "CmRSAAAAlK1Sf_gq_k_s6RGkqoUpdhTiOWWutYTjiwFGIo-YQUyFccZ4durjitVJWAQf1Sgk19g6tHHcPLrvdmmUob75LQIY0qfmkwOJOECWySnrxuf4hCkaeZA3_l58Ni99SYxNEhCmrEEEP_48LQJqUYRYNYk6GhSUZqDAYvJ2-PTbyJh4cjCbifMGqA", "name": "Chemistry", "rating": 5, "id": "979d392b613c49fbb954ee393bff65bda5042b34", "job_title": "Expertox-3", "place_id": "ChIJWxsq_4fSQIYRU9dRPmk8uIw", "address": "126 Vintage Park Blvd N, Houston, TX 77070, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.34630229999999, 29.72187359999999], "type": "Point"}, "properties": {"photos": [{"width": 4160, "height": 3120, "html_attributions": ["<a href=\"https://maps.google.com/maps/contrib/108375995272754268174/photos\">Nitish Thareja</a>"], "photo_reference": "CoQBdwAAAOj8Bvr4bKOoKY0izTFw1UtoNfusjD0I5tRwUu0_IKTEEOwOFknDkXVsAFvWb4c8SuRtsyT1cUyolqy7TWjSuHXbSB6Im3PvBM34dR6NfT9LOsl6qiw5XaArPSrs8izX3wcjBfwc7gaqK_BcKD6ylTNd6yY8Gr7HimBzVoZEQcLfEhD2xChjgOvucqas6o04MikRGhQTxfLcN4DDPnD0aw4KAwQ3wsW_aw"}], "types": ["point_of_interest", "establishment"], "reference": "CmRSAAAA3Jv5xpEev9npK7gMbSW7xNkaJw5EHTIRWunhlFnsgnnFzMTELwtGXT7ZWqGvGzyJXeArn_UqJX1VZ5fdJsd--AtzUx2FT5yTdecCK2xreIkPGx2J8n2CoTaJL3SSN69BEhBp2TTbI6ZSRcIiHn2BeTDFGhQu8GnRTufiBxnv11B7Uy5JbPJSGA", "name": "University of Houston Department of Chemistry", "rating": 5, "id": "baa83832f81135d0180e7850ce768a11f32e9df5", "job_title": "Expertox-3", "place_id": "ChIJgRkjS1G-QIYRmcpaGaD6ZeY", "address": "3585 Cullen Blvd #112, Houston, TX 77004, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.4025992, 29.7198268], "type": "Point"}, "properties": {"photos": [], "types": ["point_of_interest", "establishment"], "reference": "CmRSAAAAvBIa_MWveU6fPNDWWsrabb0Epo8BkySHMqW__w2XjpPNUsNVt4LXIR5S9t-B9J3q3CIUTUmtDETnxawEbM2AWrFHsLE4xUa_18c1MKYTsF_n0w3g_26u_UmIK3bBBfnJEhD8kESicOCXeuPXlONR8QvUGhTGMPKmaQqZNhii3g2pcM_bkixk1Q", "name": "Rice University - Department of Chemistry", "rating": 3, "id": "1553681e69a2414f5cfa7551caa2102bc22268c1", "job_title": "Expertox-3", "place_id": "ChIJL8yCnHzAQIYRZRcdAPRzhYI", "address": "6100 S Main St, Houston, TX 77005, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.4166517, 29.672442], "type": "Point"}, "properties": {"photos": [], "types": ["point_of_interest", "establishment"], "reference": "CmRSAAAA_oTemv6Zox0s5JhtSq_J2oIRRl3oakEHHfwHRh8cALh4cKPo9ikgG42MHXM-1QBLEVoVqJeqdPsbMErUy7YRKrLPA6Ct7C91TkGVtjTV9eCPnw3xenSqBGbNIq4rzZVgEhAWISc9oN4JP_dr7ogPZzhYGhTnAf8LFH-mNZ1k3KukfJ47Ndz-gg", "name": "Environmental Chemistry Inc", "rating": "NA", "id": "940f1e5d70276d8a5feaa5242d817666afa7f4b2", "job_title": "Expertox-3", "place_id": "ChIJ7UpnzJjqQIYR2qG-Hcvp_YU", "address": "2525 W Bellfort St Ste 175, Houston, TX 77054, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.57188149999999, 29.9951915], "type": "Point"}, "properties": {"photos": [{"width": 4785, "height": 3190, "html_attributions": ["<a href=\"https://maps.google.com/maps/contrib/101403699241874436061/photos\">Chemistry</a>"], "photo_reference": "CoQBdwAAAMUHQVLn0wOcHpGk4ffCH8-rAwYiREjP69P3Zr4oK2RP9DvkIDPWwhRO8zeQsFobubx2CL3eqOWhc0HFHRdtNgPxhLEPcS1a3cSBs_Cxye6RfJakSzSaopQnvdgzU4Fh8_m6WeOxAlzGqw_kWhQ-wEYZqDNF_53ORY0E-l1pQtZgEhBhnVFG9VYL5Yz2yQOV0AbuGhSf8zr89tao9f7mLT3wP3ijOeEYQA"}], "types": ["beauty_salon", "spa", "health", "clothing_store", "store", "point_of_interest", "establishment"], "reference": "CmRSAAAAcJNRZO7v_QJZsyqUQO2qi4KdQmbscfbYHNQjlq-ozHlM71HJxzLnzudtNnAHqAqkv2734MQqL_yZbYZ_YZlF0AsiCLdw2O2UEaI5eJtJnf45pyxcUIJlJ8fNkOgJSrF7EhCPakf1ROCaxC9aBibATY0RGhQm-lCslvbYcMzAt8E4Yv0VPfEEGA", "name": "Chemistry", "rating": 5, "id": "979d392b613c49fbb954ee393bff65bda5042b34", "job_title": "Arkema-Americas", "place_id": "ChIJWxsq_4fSQIYRU9dRPmk8uIw", "address": "126 Vintage Park Blvd N, Houston, TX 77070, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.34630229999999, 29.72187359999999], "type": "Point"}, "properties": {"photos": [{"width": 4160, "height": 3120, "html_attributions": ["<a href=\"https://maps.google.com/maps/contrib/108375995272754268174/photos\">Nitish Thareja</a>"], "photo_reference": "CoQBdwAAANmeXx4GPFAnR6BFisEFjoJcv0DDwbkGzNSrG9QFDCAoTzrVKdnB-57do5--Az33cASZqaG-1UHXx0-khwEZlI89wBHuSDdW5SUKDJ6iHXdtiuIb-x9l00D8Rtvdr6WwF_Y94OUb2fe5t1YJEyISBGmh7kWUB4geOEweQm_RE5aTEhD8oy_fxzwgbe7XvtHIPhv3GhSMYByKju5u4zZPHckf7wBVc50adQ"}], "types": ["point_of_interest", "establishment"], "reference": "CmRSAAAAXZuYtGdYhViqF3k5R9aByM3uASQ2-gP3GRFfHQ-B4IsvvxaV8RFUWmkG5OA3wRIcLFqCxPXglafivwwFznZECOMJf988bViGP81naN9pktZWIdW4qC_1j8GPmr8sAd4ZEhCr-5-SKp8DVxehIDjUiQz6GhTkB0u2f0bXnIu5dY33UZFeSfJSIA", "name": "University of Houston Department of Chemistry", "rating": 5, "id": "baa83832f81135d0180e7850ce768a11f32e9df5", "job_title": "Arkema-Americas", "place_id": "ChIJgRkjS1G-QIYRmcpaGaD6ZeY", "address": "3585 Cullen Blvd #112, Houston, TX 77004, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.4025992, 29.7198268], "type": "Point"}, "properties": {"photos": [], "types": ["point_of_interest", "establishment"], "reference": "CmRSAAAAXZrtzCsv7i0_SNpDrLpn6owwqO1dop3UAfxm9kZ-Anfxm5sFOX8-by6I07XIzymqDe2voirAc9i4rOz_RLk3YDQq_Gh2Vs83Iua49Ro12kJa683ueUAVQbpc5NO_nYSgEhCAqXZL6fcWtUOw2zqkT1DlGhRAcwbrhj6Ppr6EUgIZW61FEcFvEA", "name": "Rice University - Department of Chemistry", "rating": 3, "id": "1553681e69a2414f5cfa7551caa2102bc22268c1", "job_title": "Arkema-Americas", "place_id": "ChIJL8yCnHzAQIYRZRcdAPRzhYI", "address": "6100 S Main St, Houston, TX 77005, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.4166517, 29.672442], "type": "Point"}, "properties": {"photos": [], "types": ["point_of_interest", "establishment"], "reference": "CmRSAAAAYOsmYhb4-0vqmTUV0UzFLvQ3_kG0rbpwZR8q3JlngJW1MsaoMMIz9kGnWJQd62ruOEIeT2wUtXzEbQ-pncBFsS71rsM7hdZT4r0R00zcC14URBCA57mFO20WcOLl2APXEhBS6cVoMLZdj23TGMNZ98hZGhRcsyJJpNYRTM6aVD9_wmR_T-W0rA", "name": "Environmental Chemistry Inc", "rating": "NA", "id": "940f1e5d70276d8a5feaa5242d817666afa7f4b2", "job_title": "Arkema-Americas", "place_id": "ChIJ7UpnzJjqQIYR2qG-Hcvp_YU", "address": "2525 W Bellfort St Ste 175, Houston, TX 77054, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.57188149999999, 29.9951915], "type": "Point"}, "properties": {"photos": [{"width": 4785, "height": 3190, "html_attributions": ["<a href=\"https://maps.google.com/maps/contrib/101403699241874436061/photos\">Chemistry</a>"], "photo_reference": "CoQBdwAAADlT_zUkLjgJ5kPxbHqh97opUFtGRvFYivO_x5Xer9umQGnLOmdd_Kz0ye7l20fahQscXxmeYIsQFUz5ekX4KH2EYdXbMFCjTkb2CvTcO3QoyIfAolFNtT8rI-uLfx-9FRjaLUkU9D9RDtJEG32hlXmPiTvvhkQoVRlTbYj3geLKEhBIVp83cyNVhNeiIactQSnCGhQobDpuGk18mCZPzTTwBbSC7MfL3w"}], "types": ["beauty_salon", "spa", "health", "clothing_store", "store", "point_of_interest", "establishment"], "reference": "CmRSAAAArZCfqMDFpYEHY16AuWfcf0RjexZBsO9R_nLBdrSgA8NRj4iXfUxzXtg5o5rcnVZo9h2hIfXoFydvDC63i1IEvQFqOkfc1bgvpUhRzFvuIX04tNoSXD_LkrZCU0__0FzoEhDnADy1H-HWjVJNqB3r_NIZGhTgU6tb0vTXxWVbk5F03hjW1tHO6g", "name": "Chemistry", "rating": 5, "id": "979d392b613c49fbb954ee393bff65bda5042b34", "job_title": "Ascend-Performance-Materials", "place_id": "ChIJWxsq_4fSQIYRU9dRPmk8uIw", "address": "126 Vintage Park Blvd N, Houston, TX 77070, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.34630229999999, 29.72187359999999], "type": "Point"}, "properties": {"photos": [{"width": 4160, "height": 3120, "html_attributions": ["<a href=\"https://maps.google.com/maps/contrib/108375995272754268174/photos\">Nitish Thareja</a>"], "photo_reference": "CoQBdwAAAFE8rSSv_46dhaeeFQixLGsumpa3JsO8UyZG1wKFuB4-2AiKcEJYcA9qvV0g_5IYAGiArKxD_FssQ1YKupBImQ0koRhIZwjSCxaokW76d_E5TypV65MeldXYyBp_hMvwe28AkwK_XT9-pWSsGCFp5oF_QPVisqn77sKDzBjakecoEhB2bL647vTv8tzxCKKFrSMjGhS1Mq0j8GLejBcIc9xcC0XK7pkTWQ"}], "types": ["point_of_interest", "establishment"], "reference": "CmRSAAAAxsEYbjyu0uWRmYbGizbsdrsrE9CBLnoIgeBSukomPgZf7tRq7pxywyfQyfo5puklOXDEbYre3TcgN4-8QYrSQOJ9QbyttdYzJzOuC9nBA4HQ3EQeOxOclVvhZSom0tCYEhAZ-QdTtNSkl6cTW0bFnFDxGhSdJ6NyN8VZqwj93mbKA9UX_XKkTQ", "name": "University of Houston Department of Chemistry", "rating": 5, "id": "baa83832f81135d0180e7850ce768a11f32e9df5", "job_title": "Ascend-Performance-Materials", "place_id": "ChIJgRkjS1G-QIYRmcpaGaD6ZeY", "address": "3585 Cullen Blvd #112, Houston, TX 77004, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.4025992, 29.7198268], "type": "Point"}, "properties": {"photos": [], "types": ["point_of_interest", "establishment"], "reference": "CmRSAAAAakabz_CcHFPmfRc-7_zYA6eT4iPFNRRkO9dcLGGOgpecLZEoFRWU3YtDuINrkZYMWk4fX0VcS9hpO-eH7q2CnG3lOsCqEYbjxlnC-sCo3zg4Iwk7_Ptx6tsA-w165nA_EhCLalPzR3YBSiIJYPLMzGdyGhQALfbMGGZGgtaLkpY8xeF9IK7wTw", "name": "Rice University - Department of Chemistry", "rating": 3, "id": "1553681e69a2414f5cfa7551caa2102bc22268c1", "job_title": "Ascend-Performance-Materials", "place_id": "ChIJL8yCnHzAQIYRZRcdAPRzhYI", "address": "6100 S Main St, Houston, TX 77005, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.4166517, 29.672442], "type": "Point"}, "properties": {"photos": [], "types": ["point_of_interest", "establishment"], "reference": "CmRSAAAAyqESuZmQDOIrICpbDctvc8KmN0b3zsHGDbEg9JcydXxAr9_4Nmt6o0GjXa3-lS9f1tf0WIIjRRLmaUg-q6MX4LtNhtS8_QyAqvbkAOOKLqotaX9XTGPo7Bo-vuPMUYuGEhB3aym6Il431RHl5Y98n_47GhT5ASZ-Xtq_ZH2snaTPW-s0OF6EGw", "name": "Environmental Chemistry Inc", "rating": "NA", "id": "940f1e5d70276d8a5feaa5242d817666afa7f4b2", "job_title": "Ascend-Performance-Materials", "place_id": "ChIJ7UpnzJjqQIYR2qG-Hcvp_YU", "address": "2525 W Bellfort St Ste 175, Houston, TX 77054, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.57188149999999, 29.9951915], "type": "Point"}, "properties": {"photos": [{"width": 4785, "height": 3190, "html_attributions": ["<a href=\"https://maps.google.com/maps/contrib/101403699241874436061/photos\">Chemistry</a>"], "photo_reference": "CoQBdwAAAAcV-OjaOZZLG6_1uTco6SzwwASyuysQSsBjpv6N8TSKI4cu2sbZ9UtH0T5iOzbbdcDpP6Pm66jAWhw4h5xYk-SDI2qXcJ5-6s19H7pVQzemdXMboc_D6YUmsesSHJW8qIQaIPwscWA3j6GFpJBA29hlx5ls9TdIOD9oVb0p0_ziEhCQMl93T1cohSVE8bps-FDBGhTcuvsVg70KRzWBQUDfqgEdvcbhmQ"}], "types": ["beauty_salon", "spa", "health", "clothing_store", "store", "point_of_interest", "establishment"], "reference": "CmRSAAAAsabssbBBNYpDp2kMHtAjcRTZqzHDPh2Pilr0eBphGmxP1o0axxtlWhF5S-87SYJIPtg3nlCIXOLcZf2V461TatwHjcFc0xe-PC0z23Ws7vEm4Jsj_FC6e1AAfR4_MDSSEhAOQn-sm3AQcY3U-GHv56vGGhRRcsxWPJuUxIjKkiYZg3fuIE6zkg", "name": "Chemistry", "rating": 5, "id": "979d392b613c49fbb954ee393bff65bda5042b34", "job_title": "St.-Joseph-Medical-Center", "place_id": "ChIJWxsq_4fSQIYRU9dRPmk8uIw", "address": "126 Vintage Park Blvd N, Houston, TX 77070, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.34630229999999, 29.72187359999999], "type": "Point"}, "properties": {"photos": [{"width": 4160, "height": 3120, "html_attributions": ["<a href=\"https://maps.google.com/maps/contrib/108375995272754268174/photos\">Nitish Thareja</a>"], "photo_reference": "CoQBdwAAAMF3EFDN52gmcEDoFLCQxqZuSRlGGvzeCYJx9DkCcXBOKUDmBXW6U8peNSMeCgCIaazk4NikK-ZRPkhBs9yWC-rEDxAN7fI43v1RHVHe1s31jbSzmwUeKM28UAIgx8uBN4q4V2UP-YSGh5gP6_H6X4jC1NtneAJVin2ph4f4eMIOEhCIF_j12peKI2zjFsGnulLLGhT0tCkbIX9EnLrc5cpR5niKIJXa-g"}], "types": ["point_of_interest", "establishment"], "reference": "CmRSAAAAATVRAtn--_1u1jOrS8i-dviaAIWKCIv9vYvA7Lb0IrZWBBUDpnCS5tCtviHRicadab8Rd1Ax5D28_-vSSVPKrT7IDh786Pw6FZ80NwFkPqRjxOorhBjUnj3SuZyjCERLEhDyQX4GiGCqxJZEXBhDk6siGhQjyrLfrkkkvpbIzFfv8wuQuVvA9A", "name": "University of Houston Department of Chemistry", "rating": 5, "id": "baa83832f81135d0180e7850ce768a11f32e9df5", "job_title": "St.-Joseph-Medical-Center", "place_id": "ChIJgRkjS1G-QIYRmcpaGaD6ZeY", "address": "3585 Cullen Blvd #112, Houston, TX 77004, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.4025992, 29.7198268], "type": "Point"}, "properties": {"photos": [], "types": ["point_of_interest", "establishment"], "reference": "CmRSAAAAJ_Ciob-zdykO5BqFS8-Ifg1snwzATbe53U_bC8W-EovLmbHc0unkvWawJQwIkQeE1wOCkPmblgUOOMlvT7sVxn1znG1tCvE_K2d0TgIX_DKs3Ycw1dq1or5NckcYSLWXEhBSaNJxd_dgrM5IscmH95DvGhSph8dqATs9_4ugomuQYhvAX2an-A", "name": "Rice University - Department of Chemistry", "rating": 3, "id": "1553681e69a2414f5cfa7551caa2102bc22268c1", "job_title": "St.-Joseph-Medical-Center", "place_id": "ChIJL8yCnHzAQIYRZRcdAPRzhYI", "address": "6100 S Main St, Houston, TX 77005, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.4166517, 29.672442], "type": "Point"}, "properties": {"photos": [], "types": ["point_of_interest", "establishment"], "reference": "CmRSAAAAaBjxr77otym6q7cCehE3gf3ldC9WAdHUP_7h8awrOzkcTRykzYRwrfLSl1w3U40l3UYI-VZR16zhNCZNwofzxSfEzpQsbFeW29XjZWxZSmy7xQyHCB8t92a7Fl2WHCopEhAewYpiDsAOMgfbJO3ReX-KGhRoMcq4YQ9lJVwYBs9F8pwY9Z5Xxw", "name": "Environmental Chemistry Inc", "rating": "NA", "id": "940f1e5d70276d8a5feaa5242d817666afa7f4b2", "job_title": "St.-Joseph-Medical-Center", "place_id": "ChIJ7UpnzJjqQIYR2qG-Hcvp_YU", "address": "2525 W Bellfort St Ste 175, Houston, TX 77054, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.57188149999999, 29.9951915], "type": "Point"}, "properties": {"photos": [{"width": 4785, "height": 3190, "html_attributions": ["<a href=\"https://maps.google.com/maps/contrib/101403699241874436061/photos\">Chemistry</a>"], "photo_reference": "CoQBdwAAAOt4AnKhiz9oqVfz65-yxvFFqr5OsDLD4Ii0AGkrH1ItCc35eQXPQC5t_ZgD9OXbJNi7Z5Cxu2LfDKpEVdgl2i5c9fGOesQT1N4KWudNS-5cK4vLn_3MlzmjrGMesvVOpKXzuOwPdV7DOG8T2j5UAf2cKuy0KOonpZsKE8BLPa2fEhD1wzmJeCp0rzdmxaXUrGiqGhTCpjM4eYqO-Eu2Vajg1Em_gJCOww"}], "types": ["beauty_salon", "spa", "health", "clothing_store", "store", "point_of_interest", "establishment"], "reference": "CmRSAAAAeq7e5-N_fx9M1KzoIDVMcYrgFHaGqfoZPjVb3_FJLAGsixV6DLX8HU9hKEVuB-nQh3cnT2IEpiF9oAcTUhpya_07z_wEcX7RsPe8i22wbWyNy3IeXJQ1ugt3DCjHdfpiEhA23Fko6wFCINUKZDLfxpvlGhQspE1y7WhWCvhB4EkY8hLk68fb5A", "name": "Chemistry", "rating": 5, "id": "979d392b613c49fbb954ee393bff65bda5042b34", "job_title": "Legacy-Medsearch", "place_id": "ChIJWxsq_4fSQIYRU9dRPmk8uIw", "address": "126 Vintage Park Blvd N, Houston, TX 77070, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.34630229999999, 29.72187359999999], "type": "Point"}, "properties": {"photos": [{"width": 4160, "height": 3120, "html_attributions": ["<a href=\"https://maps.google.com/maps/contrib/108375995272754268174/photos\">Nitish Thareja</a>"], "photo_reference": "CoQBdwAAAEsen_TDQaf194ukAliEMZhkKmPQ5Ikutk-SvgCT04m_ASEEATI4iHNbdDnq_XQlgmmxrf_K4Z91DiMpsv5DoXcHZEllsvvr_OQoBBe2pIaV0ONep6dWf5y5p-3KeISOckb_rlDZF5SN8WvwBMzuBn-UUTDSoquYPnhsyEYGwcvHEhDN-A62KpNarxh4qACdxYKEGhRCFzN3BgWiG3ZnpIwclDMcOdXt6g"}], "types": ["point_of_interest", "establishment"], "reference": "CmRSAAAA-XDMuMGKy1cOj7mFNPaG7xSnb3IwN2aR5JMsL_XVi7xBCfZZpzIp4PJXU9toEOMJiwVSrsJqFdflIp9uQwTl5YCBT_NlH2zrJe54jFvivZauRTZ8BpdpTV13Vbdce862EhA49g-K4DQmKVFM5rnhmEj3GhRcs84Gjx5DziYkUOh8PfBTBQTJVQ", "name": "University of Houston Department of Chemistry", "rating": 5, "id": "baa83832f81135d0180e7850ce768a11f32e9df5", "job_title": "Legacy-Medsearch", "place_id": "ChIJgRkjS1G-QIYRmcpaGaD6ZeY", "address": "3585 Cullen Blvd #112, Houston, TX 77004, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.4025992, 29.7198268], "type": "Point"}, "properties": {"photos": [], "types": ["point_of_interest", "establishment"], "reference": "CmRSAAAANdEmM8NBCBUXsVgizj8cOiRvhVIrhTbmUHdRERVJWOgYW3HJ71KJW6XElvnW-8FyJOL4l2BO004KZ0c3DWWKLplJc_9hzg6rNpw9eJDyENYiYULwz5d9WWslkYKhVPLjEhDU0Avhy7-AiTOEOSk6EnA3GhROYGJcq0sPrg5ELIjstgiGVK6eBQ", "name": "Rice University - Department of Chemistry", "rating": 3, "id": "1553681e69a2414f5cfa7551caa2102bc22268c1", "job_title": "Legacy-Medsearch", "place_id": "ChIJL8yCnHzAQIYRZRcdAPRzhYI", "address": "6100 S Main St, Houston, TX 77005, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.4166517, 29.672442], "type": "Point"}, "properties": {"photos": [], "types": ["point_of_interest", "establishment"], "reference": "CmRSAAAAlnT9oJb0mh-YTXp49jHRWOO6uxuYeLqxl9SMY-giXcsnvoVeGQTurDY2CrcY_GzJgy36tvxoEU2q9WNCXSpxqWH0rrXqF8cj-QOARR-eRX_kigvHQyj5BLB3ogDScKYbEhAZA5ZFtV2id_RRwxn3gVVvGhSrof2Op14qcIqcl7tPZGbIVkK5dg", "name": "Environmental Chemistry Inc", "rating": "NA", "id": "940f1e5d70276d8a5feaa5242d817666afa7f4b2", "job_title": "Legacy-Medsearch", "place_id": "ChIJ7UpnzJjqQIYR2qG-Hcvp_YU", "address": "2525 W Bellfort St Ste 175, Houston, TX 77054, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.57188149999999, 29.9951915], "type": "Point"}, "properties": {"photos": [{"width": 4785, "height": 3190, "html_attributions": ["<a href=\"https://maps.google.com/maps/contrib/101403699241874436061/photos\">Chemistry</a>"], "photo_reference": "CoQBdwAAAMafm0DbsoN8VzG0MbVhI48Suv_drRCBd_NI140aJwW6f3xs_2-xzLMvqywVMSIeI-75WjXp0BJB5paO1MdtpmS21BIFbc2AubxWOdLmJO8ZhkjeF3L-hJqEKVnrDjA-DExN-oH0X8EMrdOYnjLNOp-GzS5RCODVuW5aahpf7iayEhCZ15btyENVgBkAmfOETZxhGhQRHxRS091E65wkYRNjLQXz5rUWmw"}], "types": ["beauty_salon", "spa", "health", "clothing_store", "store", "point_of_interest", "establishment"], "reference": "CmRSAAAAzmZtEunJo7sVn1Kx0a2jQUrDXRms7TkV9TMScQkMa0yn0VjKx-da7ruxWsnVKFZOwakCnqNYz8kciiKgpFdEiyvA1Sb9vq6r63RCGK20BBAGVWtqaWKMAFb8L7VB4gkHEhB0Aw6Gm5SAaR2vJ97o5DpSGhT71pAeDthNQfoC79IxaQMZJf4fow", "name": "Chemistry", "rating": 5, "id": "979d392b613c49fbb954ee393bff65bda5042b34", "job_title": "The-Kinkaid-School", "place_id": "ChIJWxsq_4fSQIYRU9dRPmk8uIw", "address": "126 Vintage Park Blvd N, Houston, TX 77070, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.34630229999999, 29.72187359999999], "type": "Point"}, "properties": {"photos": [{"width": 4160, "height": 3120, "html_attributions": ["<a href=\"https://maps.google.com/maps/contrib/108375995272754268174/photos\">Nitish Thareja</a>"], "photo_reference": "CoQBdwAAAN98lyFiJPpAwvCudoQrXuhDJGnv7sARsz-WKTKyCFeLrA9C06el9HnLF-oLQH_KlYE2NAy-qLa_VT5ClTiqyUSlcciJv6iXK1ZOsCGFtqlVZngd86PeAzbk8HgkyXL4zD6aY5W78YTVTx6eDtN1IYs4jTaZak2u0-MZoRGSlRe5EhCst12taBBjsyBd8-ynMZXdGhTex9bWrWEL-qLqiZII1CU7KeZ4yQ"}], "types": ["point_of_interest", "establishment"], "reference": "CmRSAAAAogKdLF9t5mHEh6wnLQ5jA3Ij_AQlXgViCe7wXi7Q7xomNASKNeTWwGvYU5NV_YXtwVo5DaaoBg1vYr88USIzFgwJfhe1oBVJUTBTzcOevv7I27ooPswT3w602oDbBk6dEhAQH1c2TzOe995jzufyKvFKGhSVOkCPjv9CjOLpC4lg86Dxw1V5KA", "name": "University of Houston Department of Chemistry", "rating": 5, "id": "baa83832f81135d0180e7850ce768a11f32e9df5", "job_title": "The-Kinkaid-School", "place_id": "ChIJgRkjS1G-QIYRmcpaGaD6ZeY", "address": "3585 Cullen Blvd #112, Houston, TX 77004, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.4025992, 29.7198268], "type": "Point"}, "properties": {"photos": [], "types": ["point_of_interest", "establishment"], "reference": "CmRSAAAAnssBe1d85YN96ATDiqJrY7U-l4HtsdK5p4NsvYtaIgzHjsoO1VDs7Hvp7Zz60_qtN1FMSiKItMgnCJXxhRwYMyma24ejv8XgQBj2PUy9feIfR5f7OYEw79UY2v4ZowVNEhAGjnIqoHg1wGTLZBModhRfGhSkdPcPVswIIuvmg7XkkH4ZF9UBdQ", "name": "Rice University - Department of Chemistry", "rating": 3, "id": "1553681e69a2414f5cfa7551caa2102bc22268c1", "job_title": "The-Kinkaid-School", "place_id": "ChIJL8yCnHzAQIYRZRcdAPRzhYI", "address": "6100 S Main St, Houston, TX 77005, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.4166517, 29.672442], "type": "Point"}, "properties": {"photos": [], "types": ["point_of_interest", "establishment"], "reference": "CmRSAAAApiLW9Lt04Mb1yZfUlP-YV-P_KCDt_WZtOL74F-XXCpS8b6GpFAm62YrEl3uNyvuzD35wxs492AkgtcV_HBB8ctS3bwye4H8JaZ0nfJ4sh3lRqfB88XeZ_DlynCIPZj-DEhDIwUQ-eNeQuEkRXnAjKzHYGhR2wgA9v0TRorDP8Kx9gZmrvFBOOQ", "name": "Environmental Chemistry Inc", "rating": "NA", "id": "940f1e5d70276d8a5feaa5242d817666afa7f4b2", "job_title": "The-Kinkaid-School", "place_id": "ChIJ7UpnzJjqQIYR2qG-Hcvp_YU", "address": "2525 W Bellfort St Ste 175, Houston, TX 77054, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.57188149999999, 29.9951915], "type": "Point"}, "properties": {"photos": [{"width": 4785, "height": 3190, "html_attributions": ["<a href=\"https://maps.google.com/maps/contrib/101403699241874436061/photos\">Chemistry</a>"], "photo_reference": "CoQBdwAAAOXbrpDxFRz8pTi1Ozqj0Bd7hRqsnYu_poCSfCbBBUyWTJJ-AZm31yW0OPf8-QGqLODquSpzz5KINzRYdMmo54-AXLp4qyY3Y2_bgc1dQQxbAs1gEunLqW_jOvG8qF38H-nYBdDPg1ckZtEfGvikvx5SQJHmh0bWR7kGE1C9ojuxEhAZweTKdwdFq_JJVoH5OUBDGhSLBKtK5K9X14Vj4R_jZbmDGAeuqA"}], "types": ["beauty_salon", "spa", "health", "clothing_store", "store", "point_of_interest", "establishment"], "reference": "CmRSAAAAhDR-U6Hc6EcZhi6GPEW--aiI_puQi4yT2IKvls7bHuFeBzt6UO4RtYWxZeInty7WAE-5YCfT39uJmDoIckpgQpqD4sOKeA3h_rm6HTdZz-g3-gksSX2bQys2Xm3JC1BdEhAk96IAJSA5JNOaFbmyBg3PGhRj-5tdvoIUJ6elSNzDeXgk1VndUA", "name": "Chemistry", "rating": 5, "id": "979d392b613c49fbb954ee393bff65bda5042b34", "job_title": "Zimmerman-Medical-Clinic", "place_id": "ChIJWxsq_4fSQIYRU9dRPmk8uIw", "address": "126 Vintage Park Blvd N, Houston, TX 77070, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.34630229999999, 29.72187359999999], "type": "Point"}, "properties": {"photos": [{"width": 4160, "height": 3120, "html_attributions": ["<a href=\"https://maps.google.com/maps/contrib/108375995272754268174/photos\">Nitish Thareja</a>"], "photo_reference": "CoQBdwAAAAinkDHnFwi4UaMVfDULuKhZOqjjCjBk-cttT9JOe8Sxa_HKweLx1dSfriYQeW5tDQ17L9aZ1D9Y9nZfbz8Z3zVxoWXS11DxPdbO94d8vgZ_dsOCDFNiVAZKvt_L1AqJzRP-4FdOzty_BYw_vbna53vRCbPm51ns9yZyA_iVJE5cEhC745weBOeyjNObhilTbSLnGhSoUvQ0a_IhPixVB9IsEwhv3nmalw"}], "types": ["point_of_interest", "establishment"], "reference": "CmRSAAAAFjLMMmN27U_oPrWDxFjibNd8JV87d2Odeyajnn9UGDwIotbNhCBqC69ck3jnO-o7EZYKcYabEY5Zc_FcnsHFcL7fJnOcoOhKE24m0IavGEIcY1yK7tsh-8Y9Ixz_R3krEhA2cdh6oGAqKMYWdXCVYV6zGhTLKhgDjZ6kTSgv5A6FZIPkCNdmRQ", "name": "University of Houston Department of Chemistry", "rating": 5, "id": "baa83832f81135d0180e7850ce768a11f32e9df5", "job_title": "Zimmerman-Medical-Clinic", "place_id": "ChIJgRkjS1G-QIYRmcpaGaD6ZeY", "address": "3585 Cullen Blvd #112, Houston, TX 77004, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.4025992, 29.7198268], "type": "Point"}, "properties": {"photos": [], "types": ["point_of_interest", "establishment"], "reference": "CmRSAAAAFDlJ7o8QGvSL9yRqNiqGl551tJFyKBVGAWS5hGTDWSvg2gHESpxrFu8LEHjd1sBkzNtE2prUGNd9IcY9r97JI8X-d9KnkwwSvB6ch70xLaWcZmhv2lJvsqQBqVOcmojCEhA27nPekpQcY7AIXQaHSi34GhRUja5mx2RmBOhAKCB5Wak3RX1dHQ", "name": "Rice University - Department of Chemistry", "rating": 3, "id": "1553681e69a2414f5cfa7551caa2102bc22268c1", "job_title": "Zimmerman-Medical-Clinic", "place_id": "ChIJL8yCnHzAQIYRZRcdAPRzhYI", "address": "6100 S Main St, Houston, TX 77005, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.4166517, 29.672442], "type": "Point"}, "properties": {"photos": [], "types": ["point_of_interest", "establishment"], "reference": "CmRSAAAATtA_IH2RCTh18Q8nmHakEdXn4X1nbBhS3cTVDN7rZVtwsITenu_YsNi9yo2tv2CGPemnfOnOamNnE-4jmN8JylH4B-DpL59Jrw56iyNLJxdVsYyCfWoUyyon1iCAIgDHEhCg5I56OO97SHm257OIDyNiGhQS91OWCdEHxb2FzmH2-JBy2QRIcA", "name": "Environmental Chemistry Inc", "rating": "NA", "id": "940f1e5d70276d8a5feaa5242d817666afa7f4b2", "job_title": "Zimmerman-Medical-Clinic", "place_id": "ChIJ7UpnzJjqQIYR2qG-Hcvp_YU", "address": "2525 W Bellfort St Ste 175, Houston, TX 77054, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.57188149999999, 29.9951915], "type": "Point"}, "properties": {"photos": [{"width": 4785, "height": 3190, "html_attributions": ["<a href=\"https://maps.google.com/maps/contrib/101403699241874436061/photos\">Chemistry</a>"], "photo_reference": "CoQBdwAAAInHOzM2fJ8Jo0Lx-UXpJ3i7QCAQolqlsvzkSJue0MFo45OJa8jd7qLW3LsNw5ACynwOmmB661yL0jrMMtG4tfpylHJwDKHJ4ijTepXt5ukY6dtWSbJIdusM2Uu0adkSpffn4M9x2HAtkYg1l-VTH0FB9jBVgx1vcP-OrmVHtcauEhBmCN2VBNtGi9XS09_b5RDtGhQG2ZRSIJvhoBYRnqbE5GCGAIk_-A"}], "types": ["beauty_salon", "spa", "health", "clothing_store", "store", "point_of_interest", "establishment"], "reference": "CmRSAAAAdiewP2sMYWNLd-LlgzlBnExWJN7YimZAmubEbwTB7S4pNGhSNW1m29Tfdd4iLHHUTOc2o88QNtH30dh_B3ICJQqGGFR2uCZA-Il6KZttO6LQ-MH5CwzOo8Cc3rrOgLMlEhDQog3_eWrYVS7KNPsW09TTGhQE_X9rs7dqmNw7mHjWDhgkovMj0Q", "name": "Chemistry", "rating": 5, "id": "979d392b613c49fbb954ee393bff65bda5042b34", "job_title": "Md-Anderson-Cancer-Center", "place_id": "ChIJWxsq_4fSQIYRU9dRPmk8uIw", "address": "126 Vintage Park Blvd N, Houston, TX 77070, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.34630229999999, 29.72187359999999], "type": "Point"}, "properties": {"photos": [{"width": 4160, "height": 3120, "html_attributions": ["<a href=\"https://maps.google.com/maps/contrib/108375995272754268174/photos\">Nitish Thareja</a>"], "photo_reference": "CoQBdwAAAEy3O41T9uqkpNWxsQmisZRNEKH8KGt03COPGoMnUe5F7125k0Nwtuyfmhqb0Y01kZGUQnZoQrJJBYpvJmlUUI8qCI9oogJO-x_4G4LhC6RX6yZfOtgcLble7jk93U6QtTzRIqJvIIlcEewvKtbRBrgQZO1Tk8V52gO-7Zv20qQAEhCmnqs28QUch1VaI0WFBHq0GhS336GCI8FsukpP5ukMFVBGQa35Ew"}], "types": ["point_of_interest", "establishment"], "reference": "CmRSAAAAy8u0it8YGhUJNdX_-jr7VKD1YMTu6o0lXhql4QgfwzbtvRzEqM1pah02LxM7enAb7T_XSfLS_CwEJZXPZCrppVAB72pANV7BBeOJLnyDcat3vXAM5X2IDvV5wzGv1iGNEhBJMvWy-8Lq8EHS1RH4kEVxGhQIjjb7xUVQ_l3HgJ1HMBmgnERmYg", "name": "University of Houston Department of Chemistry", "rating": 5, "id": "baa83832f81135d0180e7850ce768a11f32e9df5", "job_title": "Md-Anderson-Cancer-Center", "place_id": "ChIJgRkjS1G-QIYRmcpaGaD6ZeY", "address": "3585 Cullen Blvd #112, Houston, TX 77004, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.4025992, 29.7198268], "type": "Point"}, "properties": {"photos": [], "types": ["point_of_interest", "establishment"], "reference": "CmRSAAAAMoIY3MSQWkn0zTwX8ILj49YWxrAfk4tMuEgz2f8d4v7pfyZMZu5NPn3HULRza5zV1Z2Sl_cUcldEI8hekOa6x5GiC6ghk-_evi72nuB_pzY_lM7PCSkfw119XKBfLN2-EhCtTYV2XETHTCjWW2JgdcYOGhTueCavy8-MhPehWqnv325vOv9Rrg", "name": "Rice University - Department of Chemistry", "rating": 3, "id": "1553681e69a2414f5cfa7551caa2102bc22268c1", "job_title": "Md-Anderson-Cancer-Center", "place_id": "ChIJL8yCnHzAQIYRZRcdAPRzhYI", "address": "6100 S Main St, Houston, TX 77005, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.4166517, 29.672442], "type": "Point"}, "properties": {"photos": [], "types": ["point_of_interest", "establishment"], "reference": "CmRSAAAAwdPnVilKrtM0I1Ss9gZw5yj1wE9PVQFFJPJ71OT4hI9vebEyOHH9kyPSn5CSJvVusgAnyilJwre9dB81Kmet8I1bloDkinkC9g4KJE78z7gg3a-bLVxGHa6eTNDNYMMcEhAlSGR2VShPIxCd0_ffppcQGhTQElvIAIkSxpeA47Q-xmOudageew", "name": "Environmental Chemistry Inc", "rating": "NA", "id": "940f1e5d70276d8a5feaa5242d817666afa7f4b2", "job_title": "Md-Anderson-Cancer-Center", "place_id": "ChIJ7UpnzJjqQIYR2qG-Hcvp_YU", "address": "2525 W Bellfort St Ste 175, Houston, TX 77054, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.57188149999999, 29.9951915], "type": "Point"}, "properties": {"photos": [{"width": 4785, "height": 3190, "html_attributions": ["<a href=\"https://maps.google.com/maps/contrib/101403699241874436061/photos\">Chemistry</a>"], "photo_reference": "CoQBdwAAAEvdoSKR39n_BKGlRWySmn8dIA7sKkmnXJO0m8AXSAcafcdPdpshhAX0ftaEhUP9tnPcWjLEbEiCPbyWOEkeC9bOkfSex-JI2zUejdSwNR5X-k_qBHSfI8yUGCKDN29dtlaqWmT17252hS1GLnW-crgStoZSN1FtvltCecf_rTG1EhBK3Np2GaupNeFAR5Gzk0DnGhRdBW6NWWBelb0oukszA9oikyq7lg"}], "types": ["beauty_salon", "spa", "health", "clothing_store", "store", "point_of_interest", "establishment"], "reference": "CmRSAAAA9qB1AiuixCScOm-2leA1lRsfZhi4SBmS0GaC-9bgIGyzwY0cCG3mobRXcSxdwjndPnUA6m8rmSLeAzJ037GiflMG_6qyJsP0jNFHI141_VCzAlZT6P-BNYGzyVWRTkyUEhA1AUi9IDh-lPd0E4i9YKaxGhRfG2luwo8uXfdulx2unJOFBajvtA", "name": "Chemistry", "rating": 5, "id": "979d392b613c49fbb954ee393bff65bda5042b34", "job_title": "Sysco", "place_id": "ChIJWxsq_4fSQIYRU9dRPmk8uIw", "address": "126 Vintage Park Blvd N, Houston, TX 77070, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.34630229999999, 29.72187359999999], "type": "Point"}, "properties": {"photos": [{"width": 4160, "height": 3120, "html_attributions": ["<a href=\"https://maps.google.com/maps/contrib/108375995272754268174/photos\">Nitish Thareja</a>"], "photo_reference": "CoQBdwAAAJpSoD5JCdN0lkXltvBDK2Kho5oFCZBevlFB1cC-BYGm9Vf21mAmitOX3xNLKRxPhYAQkbBTeFKbODspe1_m8WWeX-KCi0o804PkXrjAP0WBZ1qtqrxauyJRJOb8K125XJkbGuoB4PMFNzDNRv7aXuexR162lzq873RFTvSNWx4jEhABrw-UPNsCcZ_xQ5bAeo0pGhTpVLsROD4NYgvW1W1qN4Mz7LUbbA"}], "types": ["point_of_interest", "establishment"], "reference": "CmRSAAAA8R_kDZ6mvqzFLfcBm8VKjShviQ3JihyULJhc-nQPsjqRoFQaKu-j4SAeh8XtvGbn1o0a4OGYx59aOEp29PBSd5BZslJ4CUBVNzkXNjb_-BXhA4QEnRcbg_Lo1EcM6HMGEhBZ3NV7DUMVJl2XGSf7wm0pGhQe4ryh5xaIZ5fs3xMrvGAVMJS7Tg", "name": "University of Houston Department of Chemistry", "rating": 5, "id": "baa83832f81135d0180e7850ce768a11f32e9df5", "job_title": "Sysco", "place_id": "ChIJgRkjS1G-QIYRmcpaGaD6ZeY", "address": "3585 Cullen Blvd #112, Houston, TX 77004, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.4025992, 29.7198268], "type": "Point"}, "properties": {"photos": [], "types": ["point_of_interest", "establishment"], "reference": "CmRSAAAAoSz6JCuZ2MunZGGuB53_Lz_CI1_bpVFB9aUwl8w6qr7yDLHhQtDn2429fZjcwUEQB1DWlPOGxQgvjxBa8sRgg2ZSx1PQFGCydaDRsukzv_zN2PGq7ZOjJ0h4GYrWWPupEhDjdZEc4q-ovrq_4RoywFFtGhQF5NeX58cu14XStOP5KpNzQiRc_g", "name": "Rice University - Department of Chemistry", "rating": 3, "id": "1553681e69a2414f5cfa7551caa2102bc22268c1", "job_title": "Sysco", "place_id": "ChIJL8yCnHzAQIYRZRcdAPRzhYI", "address": "6100 S Main St, Houston, TX 77005, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.4166517, 29.672442], "type": "Point"}, "properties": {"photos": [], "types": ["point_of_interest", "establishment"], "reference": "CmRSAAAAgElahrNKYSSSb5iYFQZwEdOtPGMeXH8b06dRECzbOu-8IQhVFkB7up5y9Z4GPW7BQgeIdXOHqCDL7WcSh6bZ7R-nOoCCGhL6CxnAwPxQIqSbxRzM6iH14Io3SgWE6PfVEhBK0Ipk-w9lUmAbUrm6UwejGhQNVhowbD2jAP2UXgGEaEtROE-qPg", "name": "Environmental Chemistry Inc", "rating": "NA", "id": "940f1e5d70276d8a5feaa5242d817666afa7f4b2", "job_title": "Sysco", "place_id": "ChIJ7UpnzJjqQIYR2qG-Hcvp_YU", "address": "2525 W Bellfort St Ste 175, Houston, TX 77054, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.57188149999999, 29.9951915], "type": "Point"}, "properties": {"photos": [{"width": 4785, "height": 3190, "html_attributions": ["<a href=\"https://maps.google.com/maps/contrib/101403699241874436061/photos\">Chemistry</a>"], "photo_reference": "CoQBdwAAAKKiVNSWc1IDENOiNodDy5M2nPVpw-GfMEYQAZ3MLQPueTaBkragRdJEmgLLE0ssM1SzPtxtfCbS8ujdYOgadWghc9a9-IY6fqOTWsdAgFpjRqZmFzWrUuysiklRrvfqgBfgU5LK8WI5BxYR7rwXnrySRavzEyrIhgveg8bwh3nqEhAj7RF2akcx-9l6PNk6EzjaGhSeSbT3BXpBeuV-8fOSsFzfHmkvEA"}], "types": ["beauty_salon", "spa", "health", "clothing_store", "store", "point_of_interest", "establishment"], "reference": "CmRSAAAA5eZWHYhzXnxpsj7J79bmkolzYrwC27lCrqq2thJz0PSdk4aM6DmXANtePd5g1moo9Ot2RfKImi32tmhRP49Kmld_X7Bd2_fJMuLVIMZnyZdTnDlpROGObWMV4N-fiJUeEhCndX9NoVqhnW_hx4_Pc7NTGhQC0bwDT23-4-9QQQLIa61bqmy24w", "name": "Chemistry", "rating": 5, "id": "979d392b613c49fbb954ee393bff65bda5042b34", "job_title": "Clinical-Pathology-Laboratories", "place_id": "ChIJWxsq_4fSQIYRU9dRPmk8uIw", "address": "126 Vintage Park Blvd N, Houston, TX 77070, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.34630229999999, 29.72187359999999], "type": "Point"}, "properties": {"photos": [{"width": 4160, "height": 3120, "html_attributions": ["<a href=\"https://maps.google.com/maps/contrib/108375995272754268174/photos\">Nitish Thareja</a>"], "photo_reference": "CoQBdwAAAAUtI18C9eiEAOGH6M_ObogKr6NWiYiH6vhX8RTOlvvFCIB8U-4npVWzAMkzrxXpwYji5teoRqlx06nzOekA5kqPxRNqd4b6Q98J2TFCo9ulO1h2Um-y30WjqBg99oB_ZzEoAbEd6b3P22AkmPaKpyFLwHg0cRGlZz15ADcrZFs6EhAOcL60xdk3Xeme1ZxOh8EcGhRB1PE5uFE8wAvStyTFOXyTl7a_kA"}], "types": ["point_of_interest", "establishment"], "reference": "CmRSAAAAwj7HQBcvkfZF4C_GWHwAsh0wDoGyAMHF76TPUgqS41_v6Xo9JzvbOnOjhmt1IZFDrB0XjWVPdGMXRAtuO20Ac97sugGA1Nn-LrMsE8bK85OCNcKcDAhgCYTolH63JkaeEhAKDz-Sqtvu5OYEwjM5QLxXGhSC8c5aGh0Hrxxxzxn6LxqNWi0hNg", "name": "University of Houston Department of Chemistry", "rating": 5, "id": "baa83832f81135d0180e7850ce768a11f32e9df5", "job_title": "Clinical-Pathology-Laboratories", "place_id": "ChIJgRkjS1G-QIYRmcpaGaD6ZeY", "address": "3585 Cullen Blvd #112, Houston, TX 77004, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.4025992, 29.7198268], "type": "Point"}, "properties": {"photos": [], "types": ["point_of_interest", "establishment"], "reference": "CmRSAAAArgkri6pFfypyZvinjALBKAHt92Wsw5PS_l5ha1qCD1sL2Ux9q99X5xDBkKrtpPdhwdHR2MjOiuEA3BGp3C_371I6I9_ZMopKBkaECpRNf6_t5PUQqyOzDnwOLqqboJGxEhCw-xdr426brl7Lfu1ZYBZ9GhS304Rnx7625nBgKdkhcVscWstqVw", "name": "Rice University - Department of Chemistry", "rating": 3, "id": "1553681e69a2414f5cfa7551caa2102bc22268c1", "job_title": "Clinical-Pathology-Laboratories", "place_id": "ChIJL8yCnHzAQIYRZRcdAPRzhYI", "address": "6100 S Main St, Houston, TX 77005, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.4166517, 29.672442], "type": "Point"}, "properties": {"photos": [], "types": ["point_of_interest", "establishment"], "reference": "CmRSAAAAUmNfdrao-CLwOXL2tnd1RtGnCYdJMw8DsUJw4KQ3EO8Dh5GieZ48mdSgznst966OZ2OKlvxz98W5nf3a5tvT_aQXZl6AWknrehRf8tuDyF3saygmTDbhUO3UyUqNjYvZEhAV457PtqFPjluxUqfvS6iXGhSNAykgESX1ud2v6KOKFDaK6uWzhg", "name": "Environmental Chemistry Inc", "rating": "NA", "id": "940f1e5d70276d8a5feaa5242d817666afa7f4b2", "job_title": "Clinical-Pathology-Laboratories", "place_id": "ChIJ7UpnzJjqQIYR2qG-Hcvp_YU", "address": "2525 W Bellfort St Ste 175, Houston, TX 77054, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.57188149999999, 29.9951915], "type": "Point"}, "properties": {"photos": [{"width": 4785, "height": 3190, "html_attributions": ["<a href=\"https://maps.google.com/maps/contrib/101403699241874436061/photos\">Chemistry</a>"], "photo_reference": "CoQBdwAAAHihFxkRIQEuVRakzOlGqT5KhSlzPtGIsrslJ5VMJxedwEpAkAboMvkAWlb4-2Ye5lbufDF9Ig2r_sLKVIDBHfYopeTotJK8TZN-SWN-gcuyx4V2ahU--ZKlFxHSsbCFh-xLvSfgmw3ZC9ZEQWJmolc54Quewy5sHRcB2XEU5kOhEhCXFxCO_J9IsSUKp0IiPCZpGhSol-tcrD-r1q5iSFhU9hfpc-yUgA"}], "types": ["beauty_salon", "spa", "health", "clothing_store", "store", "point_of_interest", "establishment"], "reference": "CmRSAAAASBper6VwQ91MveR-5p-EQkxzg6jUgjHj8EZT5Kv7AXVwJkQwgNvhDbMIkDLlw-mCXrejUGkS3YL4oyQDG535awkpDvzNGBY02FD-LIdXdd3xrQZPUjg8HU65X8fA9tUzEhAFo_2bQ0W3W5kLwO07xGmuGhSjZQRFX8fudJcd2nEwKWYWIbHTMA", "name": "Chemistry", "rating": 5, "id": "979d392b613c49fbb954ee393bff65bda5042b34", "job_title": "Bureau-Veritas", "place_id": "ChIJWxsq_4fSQIYRU9dRPmk8uIw", "address": "126 Vintage Park Blvd N, Houston, TX 77070, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.34630229999999, 29.72187359999999], "type": "Point"}, "properties": {"photos": [{"width": 4160, "height": 3120, "html_attributions": ["<a href=\"https://maps.google.com/maps/contrib/108375995272754268174/photos\">Nitish Thareja</a>"], "photo_reference": "CoQBdwAAAMcmFtG2EbkK7STYyLxnk4D7SSKTRgjERoa5a54lll_mbvEerLsHfeMI0z8GNn5UU6kLhehigQkxgXa4qQRiCYKWqEY1IFi38FnMveR8nhVn-0dZzamN8q_v0KCdBTm7cHt0ZpnO-zVDK3QskIzOowF77sdVHC0n2X_LFC7OVxxBEhCAw0z6jztdlLm5VAH9lJc_GhQ5znO0WfL7vKXWZ3otzHUDq029zQ"}], "types": ["point_of_interest", "establishment"], "reference": "CmRSAAAAdIU9oLyWqqmadP1iK9ODpgFFHCneBhxfwAG_6NicFdiJ7xbEo01mmKJyqM7fACfKShkhj2fHhvIz5Rt2UpmGQyAnjHqsCrqB-EFnNZ9YsQv7t62aYdzO5XjRnWn1AOngEhAlxY4vZRFTuvZBdto265O5GhTKXY8QROzTEzg-JlP4z4XW8dXFYg", "name": "University of Houston Department of Chemistry", "rating": 5, "id": "baa83832f81135d0180e7850ce768a11f32e9df5", "job_title": "Bureau-Veritas", "place_id": "ChIJgRkjS1G-QIYRmcpaGaD6ZeY", "address": "3585 Cullen Blvd #112, Houston, TX 77004, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.4025992, 29.7198268], "type": "Point"}, "properties": {"photos": [], "types": ["point_of_interest", "establishment"], "reference": "CmRSAAAATXHlfCxA7NV9SP2EDI0uO1_INp8O0MtQmjFr_FDeMQR3D2ovx9MmcPq4BQQcAaFBdqPgwNP08Ti8GO4oPhEzmUx5n582k4tXdMrwK3sqMcAC1yQbgh-olFboDm2ZTI_dEhCm24tCVCaNY1pYmvvlnocUGhTYc_h6qotXmPQ7Bkd0iF27dMWiNQ", "name": "Rice University - Department of Chemistry", "rating": 3, "id": "1553681e69a2414f5cfa7551caa2102bc22268c1", "job_title": "Bureau-Veritas", "place_id": "ChIJL8yCnHzAQIYRZRcdAPRzhYI", "address": "6100 S Main St, Houston, TX 77005, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.4166517, 29.672442], "type": "Point"}, "properties": {"photos": [], "types": ["point_of_interest", "establishment"], "reference": "CmRSAAAANN8gwi5wY_y-hHtLWE6bybr4n2G_mdFuFGOmb8YFz8dxZ7fxDUNjaYSx6kEixSb5JgzlRUo5E5-DgGaJv4Y_-fb20aPktysPgILj9QTEQMEbHObRc_DJ54DuD8n4kKJWEhAb_2TnNVAWNF1Jq9l8RSlEGhRsytrnuV7yFrZKSgLZCN-a9N85yw", "name": "Environmental Chemistry Inc", "rating": "NA", "id": "940f1e5d70276d8a5feaa5242d817666afa7f4b2", "job_title": "Bureau-Veritas", "place_id": "ChIJ7UpnzJjqQIYR2qG-Hcvp_YU", "address": "2525 W Bellfort St Ste 175, Houston, TX 77054, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.57188149999999, 29.9951915], "type": "Point"}, "properties": {"photos": [{"width": 4785, "height": 3190, "html_attributions": ["<a href=\"https://maps.google.com/maps/contrib/101403699241874436061/photos\">Chemistry</a>"], "photo_reference": "CoQBdwAAAGcZ3ZksttsTeiDEkjwr52-PP0b3BiPTmgN1SujrT-5YTE-JvHRcG5WnCCP9mz_6C_6UF7-DHaHtVXcke5EOndSDNloJFgXJkAYIf1EEul-6N-89XU68GQ1JxFf_sabf3qwtIsI27H0xN0PlghZcnMgZFQtIc6nlKcb8mw9_WwWmEhB5gAcqZEYJC5VKFAa9htLFGhQ1YFDPLsn2WWzbr9hdVEAdaS7uaQ"}], "types": ["beauty_salon", "spa", "health", "clothing_store", "store", "point_of_interest", "establishment"], "reference": "CmRSAAAAoWw92lTk2E69gGKzn-NCR-Xo-jmIbWAqTJ82pcIsIKvzbUBT-qPgV4xIl2ZPhELuQHH7_FvAu4exXSXWDmWXD_8ri4ddTaa6SwkQIaCxe8Fl2BQw_kSoZDOWGvD29mPUEhBLlr1F2fLgtsrNf8gi1uVZGhRP2QIHhr-bbtPiblbObINa3R2-4g", "name": "Chemistry", "rating": 5, "id": "979d392b613c49fbb954ee393bff65bda5042b34", "job_title": "Texas-Children's-Hospital", "place_id": "ChIJWxsq_4fSQIYRU9dRPmk8uIw", "address": "126 Vintage Park Blvd N, Houston, TX 77070, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.34630229999999, 29.72187359999999], "type": "Point"}, "properties": {"photos": [{"width": 4160, "height": 3120, "html_attributions": ["<a href=\"https://maps.google.com/maps/contrib/108375995272754268174/photos\">Nitish Thareja</a>"], "photo_reference": "CoQBdwAAAOyCt-gt17R9Rem98QRZkUZuzqf8DaxP2_1dVdXbIblw99NkCJRTxS20GqXDgcBzOV_0lBFupyG2fQN14YyMH3ufWc8gMUc4EL6KAbdL5Q6cTZ6Qt1j88cpAf5HI-UweaiCujanv54PBlGEi9BF-pQOGuhG2NQutAkr4GvnTDK9ZEhAMAgTVTR7X_Q5oLSRsunL_GhQGkU48s-SkgYfWGkutGzaggPXb9Q"}], "types": ["point_of_interest", "establishment"], "reference": "CmRSAAAAda9D0TFsbgRhq0FC6cWhjBcUD4udihgyraWTAccW8MFOnyBSWauDjcwP57NkxCiNWPM5dM3btwkwtYi03SQDZtTbS3EvWV0YBu1x3lLqJxi3rjflovTfKAyJcL2TVtB9EhCpE8PYFE761azjzesJ1fLOGhSwufYaufXIRDDXcsENWdv8jrRCfg", "name": "University of Houston Department of Chemistry", "rating": 5, "id": "baa83832f81135d0180e7850ce768a11f32e9df5", "job_title": "Texas-Children's-Hospital", "place_id": "ChIJgRkjS1G-QIYRmcpaGaD6ZeY", "address": "3585 Cullen Blvd #112, Houston, TX 77004, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.4025992, 29.7198268], "type": "Point"}, "properties": {"photos": [], "types": ["point_of_interest", "establishment"], "reference": "CmRSAAAA0AHSSaauPVShqJsNuj7Ul5bVPWmtC-b2mWXSDmZ_CJDYD9woVomocWcv5i-vdEQO11Ah_fYOYPc-OYv2x7sjStfQbjuR2DffQlc2utdAYa5ZNoUFM4-pRcPh56FjSykJEhB8EgJcUubJdxfFcChCE6dfGhR90FCrJDLx0BG0tqeWptoTNJ6GbA", "name": "Rice University - Department of Chemistry", "rating": 3, "id": "1553681e69a2414f5cfa7551caa2102bc22268c1", "job_title": "Texas-Children's-Hospital", "place_id": "ChIJL8yCnHzAQIYRZRcdAPRzhYI", "address": "6100 S Main St, Houston, TX 77005, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.4166517, 29.672442], "type": "Point"}, "properties": {"photos": [], "types": ["point_of_interest", "establishment"], "reference": "CmRSAAAA5IFx3i8Pvt65WDVdc9T2gsfCl2awpkK8w2ZayeMX5UbCkiswBZjAb9RFykYqy8KS6MNqM7p6q8fn4xWD7JY-amYhSpzJi0TrqsUO8wDO7L7g1P71koIrtwB0Y75r13opEhBOHFy9Xl2Z9GewChGvdrtvGhRctl0WMyFQ89uHadUDt_OQyxFgDA", "name": "Environmental Chemistry Inc", "rating": "NA", "id": "940f1e5d70276d8a5feaa5242d817666afa7f4b2", "job_title": "Texas-Children's-Hospital", "place_id": "ChIJ7UpnzJjqQIYR2qG-Hcvp_YU", "address": "2525 W Bellfort St Ste 175, Houston, TX 77054, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.57188149999999, 29.9951915], "type": "Point"}, "properties": {"photos": [{"width": 4785, "height": 3190, "html_attributions": ["<a href=\"https://maps.google.com/maps/contrib/101403699241874436061/photos\">Chemistry</a>"], "photo_reference": "CoQBdwAAAGzn2oCR4voyLzN5SyIPLMfuP4yh82kNh-_W5OSlZreLhdBQBe88089B641ZV4u-SlbF4L93dwgfG6b8gG5nNenP7iWpfpdwHQLGfam5J5hql05DzcNLoEFZTamFDC8q3Fdqtqtt8QikpFvNjRDl4N35jWgB6uqxBWsjm_2TiMJ0EhCrp7FseRvpJ5iq5CcPXiRWGhRGE3ZwVMl07vpjWWqduyY2yQVv0w"}], "types": ["beauty_salon", "spa", "health", "clothing_store", "store", "point_of_interest", "establishment"], "reference": "CmRSAAAAZXPR4EZowha30JOiyP1lEePRNAnu_nf4BQkE3wFsynRx9zQXDO8wGvM0esquuro6af0s2ZdaTYNokSih9Q5SHpRc0VCpUDa3BUOLDA-m82dboVOX20S53paMomdnPzECEhCj3Qsq7ZVYRrUB-buVD6zJGhQa7_41_f0wGvAnYOzisPYBzZllng", "name": "Chemistry", "rating": 5, "id": "979d392b613c49fbb954ee393bff65bda5042b34", "job_title": "Yes-Prep-Public-Schools", "place_id": "ChIJWxsq_4fSQIYRU9dRPmk8uIw", "address": "126 Vintage Park Blvd N, Houston, TX 77070, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.34630229999999, 29.72187359999999], "type": "Point"}, "properties": {"photos": [{"width": 4160, "height": 3120, "html_attributions": ["<a href=\"https://maps.google.com/maps/contrib/108375995272754268174/photos\">Nitish Thareja</a>"], "photo_reference": "CoQBdwAAAGwNLLzseQK6BkWvukLqJv2coDgowmixOd12_W7u5U407BXUEttpOGmzsVfZ95zsZWktMf94t7qYda9Vme_5zXf-2oPvM-Z_B3FDdMRR_89Pp1PvmF6zxroA4QWvH9_bioh7cQbw3m-VSFT9Gsw889vd_9hcCBa42icggyJyCEuREhDvX3uRTLWeE8eqKbg9d4uqGhSjnHCitGIbcfJAXLaBvJ_68rzd2A"}], "types": ["point_of_interest", "establishment"], "reference": "CmRSAAAATzH3BIdLTSVsGOXPvttVY0ES7dlxN9aaDLr0ub5vQ6Wtw16zLz5nxendk6dHwOOlcJULV6_tBh7ZyPgYUUbnEXIxx9msjHt8TCwR-4LtWO6DQcExrNOrw-M4TNSXdVPeEhC6VCqbCQXpKqFN7vs2bdBZGhSz2kP36BxldmXqrSD7b6lq-XSTUQ", "name": "University of Houston Department of Chemistry", "rating": 5, "id": "baa83832f81135d0180e7850ce768a11f32e9df5", "job_title": "Yes-Prep-Public-Schools", "place_id": "ChIJgRkjS1G-QIYRmcpaGaD6ZeY", "address": "3585 Cullen Blvd #112, Houston, TX 77004, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.4025992, 29.7198268], "type": "Point"}, "properties": {"photos": [], "types": ["point_of_interest", "establishment"], "reference": "CmRSAAAAMecjFcHVqaaa8J3RZfHH8ji7zEt_CBuqHhAOj2LMWHjP6kG1qm3zTLdlnhhazs5PSN5PYasGJNurkgobSI9Q5u4P_CVPpPpYWJR5Ic_13NXjgp4Nbesz3DIvTJfJdgKwEhC062QJDPC28q3yXLmBfuQNGhTMk5KYgZx41Ygt1f-RAYYSnuEVLA", "name": "Rice University - Department of Chemistry", "rating": 3, "id": "1553681e69a2414f5cfa7551caa2102bc22268c1", "job_title": "Yes-Prep-Public-Schools", "place_id": "ChIJL8yCnHzAQIYRZRcdAPRzhYI", "address": "6100 S Main St, Houston, TX 77005, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.4166517, 29.672442], "type": "Point"}, "properties": {"photos": [], "types": ["point_of_interest", "establishment"], "reference": "CmRSAAAAgcErahMtRlvat__34d9eE8Faq-vTv10oZoRI5Cpj4AtRo3onob1NgGFs5yS0uk_18Fe62AU9TaMyhju-F4fX13M8cRuMaDkpUZVzweksX6-uluX_XlcEVNSpsLereYHjEhAVAaaLKDWeVt9UeMMRzBhWGhRjxOkOFpsrS37VWJR0BAlQZbkSDQ", "name": "Environmental Chemistry Inc", "rating": "NA", "id": "940f1e5d70276d8a5feaa5242d817666afa7f4b2", "job_title": "Yes-Prep-Public-Schools", "place_id": "ChIJ7UpnzJjqQIYR2qG-Hcvp_YU", "address": "2525 W Bellfort St Ste 175, Houston, TX 77054, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.57188149999999, 29.9951915], "type": "Point"}, "properties": {"photos": [{"width": 4785, "height": 3190, "html_attributions": ["<a href=\"https://maps.google.com/maps/contrib/101403699241874436061/photos\">Chemistry</a>"], "photo_reference": "CoQBdwAAAA3sTL3wmoey1RtzZuUHqm5IqD__N3u3owaNgcYijZADnI9vyEGrkK-kHj59gLB8ap4LOkNOHTFznqC0WNCtB3HPygNCaeT9AigQJth-KxEwnoJYoBy5H-52o-4SRd2yayNCIGS4Vm0C0OgRJaNJz8tzCyOmkZBWlVFOhfdCY8kZEhCCkPfbJKLCppM-oV0HhU4uGhRYOxFJdZtgMeAOV-gI0cZHRXbBeQ"}], "types": ["beauty_salon", "spa", "health", "clothing_store", "store", "point_of_interest", "establishment"], "reference": "CmRSAAAAw8ptk-noqbhShAC6c6rq_hGtomentODYnHubfjLTpvr7kHy1sFma8DYNlnRGGwEtyuzoZvahq2rc-KKPNWs9bJliAVGLEZvbdQJRHhTEfmdQYbVpPNgwAVHOpD0MJs9FEhBQ1ISNj0sXBMWLBjkt81BbGhRzjky4_Qn4PPAv0pkthMS45XrLtQ", "name": "Chemistry", "rating": 5, "id": "979d392b613c49fbb954ee393bff65bda5042b34", "job_title": "Blue-Quality-Services", "place_id": "ChIJWxsq_4fSQIYRU9dRPmk8uIw", "address": "126 Vintage Park Blvd N, Houston, TX 77070, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.34630229999999, 29.72187359999999], "type": "Point"}, "properties": {"photos": [{"width": 4160, "height": 3120, "html_attributions": ["<a href=\"https://maps.google.com/maps/contrib/108375995272754268174/photos\">Nitish Thareja</a>"], "photo_reference": "CoQBdwAAAHBKM4Conu9JC4Oggg0LTu7jA3Cxpf5mU_R6fp5SxcLUApyKtnAAcnvqUuYpqZ5oVTsQoYD1lNLjQoPkwIE6vXZ72tFG_Tf6Ez730MK6hHs1-c1VM1OMfJDUwuCUOkMo8mh6mthcGfolVTTWq-o3nz-kAtKYbk6-GdsNPY_-svydEhB5P3RJ2zJn4kV4sO2ng6xqGhRXJqt83S1iw_whBt7YywyRovzbBQ"}], "types": ["point_of_interest", "establishment"], "reference": "CmRSAAAAJnL-PqRqKKER_e-XiRYHQsVkeEuYy7LBNqTH6IvbXAvf2-3-ln4qj6ivh67mBvlOTL_fQXVygHDCrUSg9ekwdHGVBTg_SLn7ltdhFJC1SLhFD-A_8Bxj7W1pvOCnoVbSEhAhjVcSeuM6blJhaqIHT3xNGhRHefFBHm7ZRq_PJ9Oy4YoQVhcnYw", "name": "University of Houston Department of Chemistry", "rating": 5, "id": "baa83832f81135d0180e7850ce768a11f32e9df5", "job_title": "Blue-Quality-Services", "place_id": "ChIJgRkjS1G-QIYRmcpaGaD6ZeY", "address": "3585 Cullen Blvd #112, Houston, TX 77004, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.4025992, 29.7198268], "type": "Point"}, "properties": {"photos": [], "types": ["point_of_interest", "establishment"], "reference": "CmRSAAAAAulzjelz2mBjaWevEjhYrPURcwOEDc4AE4QnXlw0cvB3uGsc1nt2ioBWum6b5KT8IEFkFJku_UDURtiitwBgom9RahBMryKlU8OZ0ixqdTOt65_SJs7BaCjRrPsQN787EhAQ-esI9NE85EGODkfIafotGhSC7M3g8gMkcXR2ogoYKCvryuAAJg", "name": "Rice University - Department of Chemistry", "rating": 3, "id": "1553681e69a2414f5cfa7551caa2102bc22268c1", "job_title": "Blue-Quality-Services", "place_id": "ChIJL8yCnHzAQIYRZRcdAPRzhYI", "address": "6100 S Main St, Houston, TX 77005, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.4166517, 29.672442], "type": "Point"}, "properties": {"photos": [], "types": ["point_of_interest", "establishment"], "reference": "CmRSAAAAXlZOmXNkYLLsDY0GikbvLWB89qbv1mSbYLg43Zq4_is2sahOhiWvvyiTRJuLezUkM9P8NLgF75rqMVRTne_QloRqBPGOHMSsT_Zj-00ZdFtuzMRtfqA23trfGZZJpzzhEhDR1M_WSKzw-nyA8b8lm-u3GhR-k5CA47Gki13fKVKQegf6WgSj-A", "name": "Environmental Chemistry Inc", "rating": "NA", "id": "940f1e5d70276d8a5feaa5242d817666afa7f4b2", "job_title": "Blue-Quality-Services", "place_id": "ChIJ7UpnzJjqQIYR2qG-Hcvp_YU", "address": "2525 W Bellfort St Ste 175, Houston, TX 77054, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.57188149999999, 29.9951915], "type": "Point"}, "properties": {"photos": [{"width": 4785, "height": 3190, "html_attributions": ["<a href=\"https://maps.google.com/maps/contrib/101403699241874436061/photos\">Chemistry</a>"], "photo_reference": "CoQBdwAAAH4IYUCdUB8RtTNX_z3YlXGTGtocygHVU9cCQdTkzRiCZGJcYPIZ6ZL6nts-gwNzf0yCv7cjnnEln2eBUSTRoVfDlQzkp8ij3QgVB3un7QckXJYNMFvmvhtdSKqb3Z2euDXow-U6STk_QqzJ1bd_MBRecmjghVu2TpRxDLj_fGfaEhAfDhWC__sGBLNSO9eQsJyhGhQrwCWjQ9djXSc70bG-J2OGJqN6Qw"}], "types": ["beauty_salon", "spa", "health", "clothing_store", "store", "point_of_interest", "establishment"], "reference": "CmRSAAAADNXTD62gq7jkif8Uyk-T55CbysF3gDsA8PJUlVSwNqiWiPxQiqEAYe1c5rI6jjDZNmbCrnsViUkOYL71OF_rCvNNsn9aP0S5_8MphwLmobZoTzHtqqd3XcIq5zt9CTQsEhDE_GMIuaxSafKsI59kiOYiGhTJ9N_i38LCFatvxdeT50Q7ulH79A", "name": "Chemistry", "rating": 5, "id": "979d392b613c49fbb954ee393bff65bda5042b34", "job_title": "Goose-Creek-Cisd", "place_id": "ChIJWxsq_4fSQIYRU9dRPmk8uIw", "address": "126 Vintage Park Blvd N, Houston, TX 77070, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.34630229999999, 29.72187359999999], "type": "Point"}, "properties": {"photos": [{"width": 4160, "height": 3120, "html_attributions": ["<a href=\"https://maps.google.com/maps/contrib/108375995272754268174/photos\">Nitish Thareja</a>"], "photo_reference": "CoQBdwAAAIK2u-Uzi5iW6bVo_cCKKNI5xhn-T3Yt2a8qfxJPLrCdOanN776r-1Re1ISjanhZH0g-Eesdj0xIjxJ9X7eWhw6effoYjbxgeYYbQruYaArmS0VNDX3wAqKdPfhCwDfYwA5147U89wwEi-Xe35TAlHwVFC4uEK8FVKK_7R4bkG1oEhDc4HtF6EVTxLdBOP3uItyhGhS4b15j_dp1zUsSQHPsSNP5HxKmQg"}], "types": ["point_of_interest", "establishment"], "reference": "CmRSAAAAiscyMJ_MYeqcIk_wcbYW6Zx_pE56-yscphSel8AICYsdpAy8MyMn9PrghF7BVjCFhiKOszZTUubdUfKisqnmtKz4vauVipQzSTK1M0MxBOURNA45NlPPuithQpfo8JyyEhAK2kkZEJIuPsgNkrCRy7OuGhQzCiWGyAapSa6D_CkXpqHZnU3P7A", "name": "University of Houston Department of Chemistry", "rating": 5, "id": "baa83832f81135d0180e7850ce768a11f32e9df5", "job_title": "Goose-Creek-Cisd", "place_id": "ChIJgRkjS1G-QIYRmcpaGaD6ZeY", "address": "3585 Cullen Blvd #112, Houston, TX 77004, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.4025992, 29.7198268], "type": "Point"}, "properties": {"photos": [], "types": ["point_of_interest", "establishment"], "reference": "CmRSAAAAFAfT5nH3rnHRoBpeUbBohkUV9Jk7dzVyd82tDXNSxUinXR0YNdkVtE-qpIoT7_69NoLpyuA87CM2eBzbETvN-Cc76TAEG4xsCOnnJ3u68xbzNJjyJmCLQT0JASYL7RslEhBkfI5pgkHLUl0QAyZMkgMgGhSmxS88laW7RavZuwlynIgvE3BHVw", "name": "Rice University - Department of Chemistry", "rating": 3, "id": "1553681e69a2414f5cfa7551caa2102bc22268c1", "job_title": "Goose-Creek-Cisd", "place_id": "ChIJL8yCnHzAQIYRZRcdAPRzhYI", "address": "6100 S Main St, Houston, TX 77005, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.4166517, 29.672442], "type": "Point"}, "properties": {"photos": [], "types": ["point_of_interest", "establishment"], "reference": "CmRSAAAAy8DOwgK4QdYImUdUdj3PcbhCdtI0hO6dg4fPB1emdcZQR_BXVEr6pk56E-nO7DptWHotfaFbahzEdupMPiNvbq3xfHzYWmOuJRFq7M60XHXjYUxrnQLKtx2H64Fh7t2dEhD5MUN-kreVlLtyVIsZh1BJGhRQbQTA8ymG54WU2EUpyBw7mUH5jQ", "name": "Environmental Chemistry Inc", "rating": "NA", "id": "940f1e5d70276d8a5feaa5242d817666afa7f4b2", "job_title": "Goose-Creek-Cisd", "place_id": "ChIJ7UpnzJjqQIYR2qG-Hcvp_YU", "address": "2525 W Bellfort St Ste 175, Houston, TX 77054, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.57188149999999, 29.9951915], "type": "Point"}, "properties": {"photos": [{"width": 4785, "height": 3190, "html_attributions": ["<a href=\"https://maps.google.com/maps/contrib/101403699241874436061/photos\">Chemistry</a>"], "photo_reference": "CoQBdwAAAJcAWUUzSkZY9TL3DvJd01-Ku3Amdg4iLkDpzU1JT7zxD39utw3ZQxX5cVuaieGrluN1blBWy2_p7H7DlovnmqaLXvOdqvKftxLtR90KUbxZzawgj_BXC2C9gnp2BkneilKQiEVf8nOiYH8Sjb1Imd-qGG2DpVM2VQ3eaUPyCceQEhA8-sabNBHEETSbzI4Wm64RGhTaoVle8OtK6nlkQynFlJSKR65MBA"}], "types": ["beauty_salon", "spa", "health", "clothing_store", "store", "point_of_interest", "establishment"], "reference": "CmRSAAAAYnRuCGjTAEyZAmeHeIj1h9izqmW_y4njYHAh2fxRHdlZJWQYJgUtPtnCediHWcWINoFpBhRaJJLNjOk-NYqM79tFO-ck0GHQ2lYKvEEeRwuOnycp7FikZEewYrNNGyPMEhAc1vIcGRVSxjtAdnLX6qlDGhRBeQLiJvwp8LZp7NTb-JSO5G26jA", "name": "Chemistry", "rating": 5, "id": "979d392b613c49fbb954ee393bff65bda5042b34", "job_title": "Nationwide-Laboratory-Partners-LLC", "place_id": "ChIJWxsq_4fSQIYRU9dRPmk8uIw", "address": "126 Vintage Park Blvd N, Houston, TX 77070, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.34630229999999, 29.72187359999999], "type": "Point"}, "properties": {"photos": [{"width": 4160, "height": 3120, "html_attributions": ["<a href=\"https://maps.google.com/maps/contrib/108375995272754268174/photos\">Nitish Thareja</a>"], "photo_reference": "CoQBdwAAAN1XtsvbAjUynNtFEO_poD3W1AYqatvekUoue3Omk60JoGSyhbKm2tf-OVEOBYqj-eLjvZZm_kkV-CCTXOxK4Kwgih40RwBmKrd7Ax_NI0MvPOGwY_igMcOsiQ6Ruj3yZqCEWc5Ao9au5a_5cqlD7PN_0wvZXrfO-XL4zJu6-hQEEhAm-GwP3yNDpbrpZgG1CP6oGhSFjbOQ7ZTLuWrLdm-KHAbc9KmDLw"}], "types": ["point_of_interest", "establishment"], "reference": "CmRSAAAA9sjMmYp1Q1v1GldP-i2VFCjF-l9iN8bAbna0a8FWyoXBrvtU_53v46PlLtLSXZxKzbpMhcf3cFdsusuHdkeQdqapC4NIzNxtJHyKUTb0VRlbyZP5VvyE_p9E3bO0wJCvEhDUInp28_4noOkNKPKs9pHZGhR2P4EhIjqKbeDZtbw_55CN3aFFbQ", "name": "University of Houston Department of Chemistry", "rating": 5, "id": "baa83832f81135d0180e7850ce768a11f32e9df5", "job_title": "Nationwide-Laboratory-Partners-LLC", "place_id": "ChIJgRkjS1G-QIYRmcpaGaD6ZeY", "address": "3585 Cullen Blvd #112, Houston, TX 77004, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.4025992, 29.7198268], "type": "Point"}, "properties": {"photos": [], "types": ["point_of_interest", "establishment"], "reference": "CmRSAAAAUq3OSBwJQ1hB9oPLtnniUq5Abg3V_ISFNljTwzc87bLB2Fn5r5JXHLnAtWxzE-cNCgDXNBkrN3GVuZpsnhc0Oza-z91AopN5ut8ZpeqlXfzkmSW-USYZq8ajh-W37-lYEhARKN1SjN95-AVSe9lAMrvOGhT_Qye7xQuk-vAapgpIza0yFwKSDQ", "name": "Rice University - Department of Chemistry", "rating": 3, "id": "1553681e69a2414f5cfa7551caa2102bc22268c1", "job_title": "Nationwide-Laboratory-Partners-LLC", "place_id": "ChIJL8yCnHzAQIYRZRcdAPRzhYI", "address": "6100 S Main St, Houston, TX 77005, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.4166517, 29.672442], "type": "Point"}, "properties": {"photos": [], "types": ["point_of_interest", "establishment"], "reference": "CmRSAAAAaYSl_OhZTZiHvR7v6mOWF2FO79v-Bjf-zF9MIsaa1Arhg5do5Jhu3Gd9pH6x5QTuWBlD0e1yHAe8OTu2E6KglUnQxdIbMYIH5iRX-vrW0ALff3qx_8Lb7sMAKCdv_LxkEhD3X0MN8OYWy30JLMn-nL31GhTlyvnWIgjHWWHVo-ITWR_Cm_xTjw", "name": "Environmental Chemistry Inc", "rating": "NA", "id": "940f1e5d70276d8a5feaa5242d817666afa7f4b2", "job_title": "Nationwide-Laboratory-Partners-LLC", "place_id": "ChIJ7UpnzJjqQIYR2qG-Hcvp_YU", "address": "2525 W Bellfort St Ste 175, Houston, TX 77054, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.57188149999999, 29.9951915], "type": "Point"}, "properties": {"photos": [{"width": 4785, "height": 3190, "html_attributions": ["<a href=\"https://maps.google.com/maps/contrib/101403699241874436061/photos\">Chemistry</a>"], "photo_reference": "CoQBdwAAAA7ALJ3xH3Q5UBwrEcfDEGCvc78jET9I7FPp4wR0Ur0Y1PfLWzoPn-1Ml11U1KFVq-_w1xZH17C6bP7jjsviVMbeimHv-eW3AMtyiwxaE5x5XvHWNqEPMSvnSsIUQWjI9eeKRnMm8z1DbhbJSlko0yL5gH3ozFfWBKiYswCwuWknEhCEFSAN2Ul2KfwOVBR0g9BQGhTgXwCLHZdeKNVI5OhCpxEYeSnrzA"}], "types": ["beauty_salon", "spa", "health", "clothing_store", "store", "point_of_interest", "establishment"], "reference": "CmRSAAAAtPH1uZf8of5umGFG2iZIlx5DYjK_3t13MVrjIYmhpTbc2eg6OhNVrZ-iBOi8VbugA8ZsuVM0Q3MZsF3oDnGHfUhOlfvIDlBz9xTXBpcf4SGB_VMDi4CrYauoeRMse-mvEhAm2G8Ojy1Nm8vuy1Naeu1_GhTgGHhYFHuCIbt4gPtHCXKvbln9hA", "name": "Chemistry", "rating": 5, "id": "979d392b613c49fbb954ee393bff65bda5042b34", "job_title": "Baylor-College-of-Medicine", "place_id": "ChIJWxsq_4fSQIYRU9dRPmk8uIw", "address": "126 Vintage Park Blvd N, Houston, TX 77070, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.34630229999999, 29.72187359999999], "type": "Point"}, "properties": {"photos": [{"width": 4160, "height": 3120, "html_attributions": ["<a href=\"https://maps.google.com/maps/contrib/108375995272754268174/photos\">Nitish Thareja</a>"], "photo_reference": "CoQBdwAAACg96uJz8EoQBa95X0JosNBLAzGK3JKCwnf65R4An4tq0MqwmDS_4aVJPw5KW3FtFbmNFa2HAGX6LFdcAEZP05HROZbrpZmPTeBhc9OMNaHAIBCFSHWR0Ia0OZBHY4L9bleB9jiBfF_5ahMMrlyfpO06YGFVJq-gZ6EHv_iME_PcEhBfW-bWGkyUhrhZQIMIzsk3GhQE6GWIevxvhIVo6xHLvR2iVCoynw"}], "types": ["point_of_interest", "establishment"], "reference": "CmRSAAAABlkIjE7B0niK3IPIGRVHy-29VLBx0KL0Mjvlz1K9iWEmuj7Xhum03pPiXrKfJSzcA4FF83KCwvTYIYK3ZGKrpmmdSboQzT1oBtvORwghYRQULn4Va6ucFZKczphBUrf7EhBRUlacEBKfIav0jOM6v7jrGhRstVGbf-3LHIqyQwkoXlVHYFPRnQ", "name": "University of Houston Department of Chemistry", "rating": 5, "id": "baa83832f81135d0180e7850ce768a11f32e9df5", "job_title": "Baylor-College-of-Medicine", "place_id": "ChIJgRkjS1G-QIYRmcpaGaD6ZeY", "address": "3585 Cullen Blvd #112, Houston, TX 77004, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.4025992, 29.7198268], "type": "Point"}, "properties": {"photos": [], "types": ["point_of_interest", "establishment"], "reference": "CmRSAAAAi7iqzQGdAEWskjsc2EMzh1RQA5JXXnCk_qOx0HJ8QZOXZ13i0ufruYsLInaGvIWxJL9D-Ya8TxrESUO1YogHLi3d_tZM0QTFDm77huZj8j8AdxZI29xcbAJ-953jJdR6EhDmQQwm4NTlbB6tu9X0hJnfGhStI5Jp2dRa5nKj0MI7lkMQJw0u4Q", "name": "Rice University - Department of Chemistry", "rating": 3, "id": "1553681e69a2414f5cfa7551caa2102bc22268c1", "job_title": "Baylor-College-of-Medicine", "place_id": "ChIJL8yCnHzAQIYRZRcdAPRzhYI", "address": "6100 S Main St, Houston, TX 77005, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.4166517, 29.672442], "type": "Point"}, "properties": {"photos": [], "types": ["point_of_interest", "establishment"], "reference": "CmRSAAAA-_x9hbp3bpgXixV__BnSed2EclO1lKobJN4L74pPb0yRJNg0FX5ZcYPNNrhgFznsxuJAkqI_z0q-73ZaZdlDAcQXCucrg4OL3NI7ZI3OhPC-ckM3HXlpu-TOl3oNsfYiEhD26Y09wQvTUaT3qyTE9kmgGhTwVcb4mmDoBEVRbSj69WBohx5xZQ", "name": "Environmental Chemistry Inc", "rating": "NA", "id": "940f1e5d70276d8a5feaa5242d817666afa7f4b2", "job_title": "Baylor-College-of-Medicine", "place_id": "ChIJ7UpnzJjqQIYR2qG-Hcvp_YU", "address": "2525 W Bellfort St Ste 175, Houston, TX 77054, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.57188149999999, 29.9951915], "type": "Point"}, "properties": {"photos": [{"width": 4785, "height": 3190, "html_attributions": ["<a href=\"https://maps.google.com/maps/contrib/101403699241874436061/photos\">Chemistry</a>"], "photo_reference": "CoQBdwAAADxGnKAU-h059C5PpMD1UUCZfZzeAg-4KTOrQRhegLGNZmFKAxX4Dk6GQDjUFTxz_UKEQWdDWaeuCSvuLE21ygX3Feneyl1e7yN7pDwSXmNPHBdmK4dGSeeqZghhed-YPKNFtUMZcf7MYyPqWXhTId6D5XtSKawukbdkpLPCXfclEhBgnuc51AXFnmIW3Avf28B0GhQ3-YGgWnv-ciLOMJKncMBZkDSuAw"}], "types": ["beauty_salon", "spa", "health", "clothing_store", "store", "point_of_interest", "establishment"], "reference": "CmRSAAAAK7MCOJ3i0bzg4ZU6vohFrnH4LtKHcRQMoeVyIUV_JT5dD-MYeZX5qNcQIUjov9HUp0u9E2VS-kqCl_5TdiYNR8epeCQJQsBptddBv4kXwpP7Asr_RGvnAp5Nmzv-HTn_EhAvea26AqMqEZBiaIwPnfE2GhTskj4XLPQCK1VDqPBDozsAIJaLdg", "name": "Chemistry", "rating": 5, "id": "979d392b613c49fbb954ee393bff65bda5042b34", "job_title": "Nalco-Champion%2C-An-Ecolab-Company", "place_id": "ChIJWxsq_4fSQIYRU9dRPmk8uIw", "address": "126 Vintage Park Blvd N, Houston, TX 77070, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.34630229999999, 29.72187359999999], "type": "Point"}, "properties": {"photos": [{"width": 4160, "height": 3120, "html_attributions": ["<a href=\"https://maps.google.com/maps/contrib/108375995272754268174/photos\">Nitish Thareja</a>"], "photo_reference": "CoQBdwAAAKAYSyYMQ0dPvRHtxyRuD88SFoz1rwyuM8d9UYZqCkKMg75QKFodIl5w2ufRJbN4RJaeeh_lNZkoOoEM4VEO5L3d_yc2hSv0_q3mh1_7eKVbsoaUQEwz-OWSDAJwcLhYkXoVGHFNUjYBErqqkbP5qiAf2yFa7TiDfqRcGSmmVsVyEhBqIH6BSxp2ctaYY7--Ye_uGhRFp15kyjAakE-aM1bcAX7yfvqxbQ"}], "types": ["point_of_interest", "establishment"], "reference": "CmRSAAAAr8gwcGuDJj1q6uZYib5lU3TZZdEhgOzG2gs3piH-jioGfoQ_64q__xxoFZtfHU-Xq6ACZ16qAgW78SJOmt3Ac0awdlJ_CA9R7dZ5cx-8eNj8Be63ATSXkUx3H-mciD1aEhAXfk6xrJvpfa9UFm-95ioEGhSbSZVlAwLlJtnBYUtMkZOkq_w3vA", "name": "University of Houston Department of Chemistry", "rating": 5, "id": "baa83832f81135d0180e7850ce768a11f32e9df5", "job_title": "Nalco-Champion%2C-An-Ecolab-Company", "place_id": "ChIJgRkjS1G-QIYRmcpaGaD6ZeY", "address": "3585 Cullen Blvd #112, Houston, TX 77004, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.4025992, 29.7198268], "type": "Point"}, "properties": {"photos": [], "types": ["point_of_interest", "establishment"], "reference": "CmRSAAAAzaD9sZGCnV8GFyq4LvSGaQ8oA-XOBSpAXFeQYrd59lDrlwzS7zJBQodbFMVMENPbMMKDLXYVSLRS1lafd5vxMJ7ySWJHBZhyVLna3pMcmD9M1rJCvW69N949kqKZBzeWEhDynWSNbQhW597O50QYLqQVGhSAVr1C6Xix99CLW6gKSUtTKX7RIA", "name": "Rice University - Department of Chemistry", "rating": 3, "id": "1553681e69a2414f5cfa7551caa2102bc22268c1", "job_title": "Nalco-Champion%2C-An-Ecolab-Company", "place_id": "ChIJL8yCnHzAQIYRZRcdAPRzhYI", "address": "6100 S Main St, Houston, TX 77005, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.4166517, 29.672442], "type": "Point"}, "properties": {"photos": [], "types": ["point_of_interest", "establishment"], "reference": "CmRSAAAARgw6K23AE46cc04Umti8Kygck9qfTnLgWeQ9QwEQ1EO_YL2PbpCE45O8ebauwOF3d8pm1Rn14Q6gkUwI9WtpoCA4x-fVova20EdjVFHxJsc9xkPYppPXkBM50IBAOINCEhBrjQFH5ZApehWpHYgt1V0rGhQ0NMP0UjofwrlioCPhIWWPPHE3wA", "name": "Environmental Chemistry Inc", "rating": "NA", "id": "940f1e5d70276d8a5feaa5242d817666afa7f4b2", "job_title": "Nalco-Champion%2C-An-Ecolab-Company", "place_id": "ChIJ7UpnzJjqQIYR2qG-Hcvp_YU", "address": "2525 W Bellfort St Ste 175, Houston, TX 77054, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.57188149999999, 29.9951915], "type": "Point"}, "properties": {"photos": [{"width": 4785, "height": 3190, "html_attributions": ["<a href=\"https://maps.google.com/maps/contrib/101403699241874436061/photos\">Chemistry</a>"], "photo_reference": "CoQBdwAAAI7_MVq0MzIXEISNgZYtM3hGq-3JvfNQDwQuOXIbzVkMk9Nwi8qQopwP-rwKaS1MY3StSivZjhQeYtwg4ReV_ENIBWcWqfizZvR9C_EA0pYrBvDADLfSVy3vpxZJWrm29qERtPcoDqr-69UQhFoL5BAswpOLRbulA3rZNA670ca6EhB9s8CknLy_sR5mRILdIMzuGhSk-arV_cBn39FfLWcDMl6edncF4w"}], "types": ["beauty_salon", "spa", "health", "clothing_store", "store", "point_of_interest", "establishment"], "reference": "CmRSAAAAGzska6G2MIUKLiFaUD6d9ZWLV4Ynd4x_azEFsi_KmBijBuN_ojpSP3QyWoVhI1AvhEfR6IHJc3YXc3SHexYJwLaJ441iB-aeOi95DR3qJ4mYpst1GCte6SZDHAYVv_FpEhCrGPX6s3v5q7836kX1pSShGhSvsFDW0Gdd0H5bN-BJo4MW1ycomw", "name": "Chemistry", "rating": 5, "id": "979d392b613c49fbb954ee393bff65bda5042b34", "job_title": "Hexion-Inc.", "place_id": "ChIJWxsq_4fSQIYRU9dRPmk8uIw", "address": "126 Vintage Park Blvd N, Houston, TX 77070, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.34630229999999, 29.72187359999999], "type": "Point"}, "properties": {"photos": [{"width": 4160, "height": 3120, "html_attributions": ["<a href=\"https://maps.google.com/maps/contrib/108375995272754268174/photos\">Nitish Thareja</a>"], "photo_reference": "CoQBdwAAAP97kkkPypZ-WzvCRka1ituTZfFX9x8-hV605__-UA3bRAzvl-xg_AY2rFzs5qL0DbAjVpBGtTmOHwhYtt0ljsmGhoA5Zd99VbrC54g0RLVWw3RD5sGOilYDJ7Y-ltkzmVvVEOw3WchbsnNuE_P9Aqcc1pfzlfSknBAcATHGKFX9EhBMWhQnC61MLP-05ktTSvcTGhRcPJuHwmZnW9OEDW_EzlW_WXj0PQ"}], "types": ["point_of_interest", "establishment"], "reference": "CmRSAAAAP6sXscOWgBCSmfzWXI8nAqxTqKv0amMHwwWwkGuW_nnmDyidf2GwPKLjX9A9vyuJ7fatpH9EP4CHKIUQFI-NfGLw97s6ieFqxUK-ezliU-t113Ljl2hFD01FuIJeN7uPEhAh22aqGPgAIEmu9_IIDQfWGhSUo31ThE4nS1xNhbzTB5Vke0BX2w", "name": "University of Houston Department of Chemistry", "rating": 5, "id": "baa83832f81135d0180e7850ce768a11f32e9df5", "job_title": "Hexion-Inc.", "place_id": "ChIJgRkjS1G-QIYRmcpaGaD6ZeY", "address": "3585 Cullen Blvd #112, Houston, TX 77004, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.4025992, 29.7198268], "type": "Point"}, "properties": {"photos": [], "types": ["point_of_interest", "establishment"], "reference": "CmRSAAAAumCTkfILomPBosjlAmtHsJtjgol6hBGmhIUtDmT6SFpe7v34690kXM7grZOB78ptAq_bw3OBRcgSjbylvMGrFzob6_eXgm1ay9oBqb1472ZXJ2tMTe8O55TpXC24cBh-EhDSeb2K4uD3HBsornLVNSc3GhTTU2jXNQk-UrEWkE7ewblNm7gp-Q", "name": "Rice University - Department of Chemistry", "rating": 3, "id": "1553681e69a2414f5cfa7551caa2102bc22268c1", "job_title": "Hexion-Inc.", "place_id": "ChIJL8yCnHzAQIYRZRcdAPRzhYI", "address": "6100 S Main St, Houston, TX 77005, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.4166517, 29.672442], "type": "Point"}, "properties": {"photos": [], "types": ["point_of_interest", "establishment"], "reference": "CmRSAAAA-TZNTu-s8dbDAGUgBvcKUjZYXQpfeva2HSug1zAoi6txuil-3KTNaKiFbkoJq0MRdh3_UfM3yLoRPE94QoyKMPrfBpqpopxMGiecbH0wagIAOg-AoeBE_5au5gT0XXyyEhBsJ8t_F9POwUXS3JUuE23fGhQrVOVDjRaSGjj9n9s_LJyPfcpBDg", "name": "Environmental Chemistry Inc", "rating": "NA", "id": "940f1e5d70276d8a5feaa5242d817666afa7f4b2", "job_title": "Hexion-Inc.", "place_id": "ChIJ7UpnzJjqQIYR2qG-Hcvp_YU", "address": "2525 W Bellfort St Ste 175, Houston, TX 77054, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.57188149999999, 29.9951915], "type": "Point"}, "properties": {"photos": [{"width": 4785, "height": 3190, "html_attributions": ["<a href=\"https://maps.google.com/maps/contrib/101403699241874436061/photos\">Chemistry</a>"], "photo_reference": "CoQBdwAAAMafm0DbsoN8VzG0MbVhI48Suv_drRCBd_NI140aJwW6f3xs_2-xzLMvqywVMSIeI-75WjXp0BJB5paO1MdtpmS21BIFbc2AubxWOdLmJO8ZhkjeF3L-hJqEKVnrDjA-DExN-oH0X8EMrdOYnjLNOp-GzS5RCODVuW5aahpf7iayEhCZ15btyENVgBkAmfOETZxhGhQRHxRS091E65wkYRNjLQXz5rUWmw"}], "types": ["beauty_salon", "spa", "health", "clothing_store", "store", "point_of_interest", "establishment"], "reference": "CmRSAAAAzmZtEunJo7sVn1Kx0a2jQUrDXRms7TkV9TMScQkMa0yn0VjKx-da7ruxWsnVKFZOwakCnqNYz8kciiKgpFdEiyvA1Sb9vq6r63RCGK20BBAGVWtqaWKMAFb8L7VB4gkHEhB0Aw6Gm5SAaR2vJ97o5DpSGhT71pAeDthNQfoC79IxaQMZJf4fow", "name": "Chemistry", "rating": 5, "id": "979d392b613c49fbb954ee393bff65bda5042b34", "job_title": "Houston-Baptist-University", "place_id": "ChIJWxsq_4fSQIYRU9dRPmk8uIw", "address": "126 Vintage Park Blvd N, Houston, TX 77070, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.34630229999999, 29.72187359999999], "type": "Point"}, "properties": {"photos": [{"width": 4160, "height": 3120, "html_attributions": ["<a href=\"https://maps.google.com/maps/contrib/108375995272754268174/photos\">Nitish Thareja</a>"], "photo_reference": "CoQBdwAAAN98lyFiJPpAwvCudoQrXuhDJGnv7sARsz-WKTKyCFeLrA9C06el9HnLF-oLQH_KlYE2NAy-qLa_VT5ClTiqyUSlcciJv6iXK1ZOsCGFtqlVZngd86PeAzbk8HgkyXL4zD6aY5W78YTVTx6eDtN1IYs4jTaZak2u0-MZoRGSlRe5EhCst12taBBjsyBd8-ynMZXdGhTex9bWrWEL-qLqiZII1CU7KeZ4yQ"}], "types": ["point_of_interest", "establishment"], "reference": "CmRSAAAAogKdLF9t5mHEh6wnLQ5jA3Ij_AQlXgViCe7wXi7Q7xomNASKNeTWwGvYU5NV_YXtwVo5DaaoBg1vYr88USIzFgwJfhe1oBVJUTBTzcOevv7I27ooPswT3w602oDbBk6dEhAQH1c2TzOe995jzufyKvFKGhSVOkCPjv9CjOLpC4lg86Dxw1V5KA", "name": "University of Houston Department of Chemistry", "rating": 5, "id": "baa83832f81135d0180e7850ce768a11f32e9df5", "job_title": "Houston-Baptist-University", "place_id": "ChIJgRkjS1G-QIYRmcpaGaD6ZeY", "address": "3585 Cullen Blvd #112, Houston, TX 77004, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.4025992, 29.7198268], "type": "Point"}, "properties": {"photos": [], "types": ["point_of_interest", "establishment"], "reference": "CmRSAAAAnssBe1d85YN96ATDiqJrY7U-l4HtsdK5p4NsvYtaIgzHjsoO1VDs7Hvp7Zz60_qtN1FMSiKItMgnCJXxhRwYMyma24ejv8XgQBj2PUy9feIfR5f7OYEw79UY2v4ZowVNEhAGjnIqoHg1wGTLZBModhRfGhSkdPcPVswIIuvmg7XkkH4ZF9UBdQ", "name": "Rice University - Department of Chemistry", "rating": 3, "id": "1553681e69a2414f5cfa7551caa2102bc22268c1", "job_title": "Houston-Baptist-University", "place_id": "ChIJL8yCnHzAQIYRZRcdAPRzhYI", "address": "6100 S Main St, Houston, TX 77005, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.4166517, 29.672442], "type": "Point"}, "properties": {"photos": [], "types": ["point_of_interest", "establishment"], "reference": "CmRSAAAApiLW9Lt04Mb1yZfUlP-YV-P_KCDt_WZtOL74F-XXCpS8b6GpFAm62YrEl3uNyvuzD35wxs492AkgtcV_HBB8ctS3bwye4H8JaZ0nfJ4sh3lRqfB88XeZ_DlynCIPZj-DEhDIwUQ-eNeQuEkRXnAjKzHYGhR2wgA9v0TRorDP8Kx9gZmrvFBOOQ", "name": "Environmental Chemistry Inc", "rating": "NA", "id": "940f1e5d70276d8a5feaa5242d817666afa7f4b2", "job_title": "Houston-Baptist-University", "place_id": "ChIJ7UpnzJjqQIYR2qG-Hcvp_YU", "address": "2525 W Bellfort St Ste 175, Houston, TX 77054, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.57188149999999, 29.9951915], "type": "Point"}, "properties": {"photos": [{"width": 4785, "height": 3190, "html_attributions": ["<a href=\"https://maps.google.com/maps/contrib/101403699241874436061/photos\">Chemistry</a>"], "photo_reference": "CoQBdwAAAHyT6PokDJ8wYKnkxzB5bLND9Ys4vbCS7p-dr-JWlSInFbgGLpHa5RAfPu19IFC1SQ7yif0DPsPz2LCvGb2wbfNYPZ8hPkrl8tKeXRmbvGsN3-ThoF4nhhCokRvnqr1nrtw2F5LmQA9-T32ZkKdE6L18AG2vFMUAdoZEmMJ6nfNLEhChcIVGEgmLEcw6wN2dp6OXGhSbcPKV8xJC5IH5Aipu1AP0ZfpnDg"}], "types": ["beauty_salon", "spa", "health", "clothing_store", "store", "point_of_interest", "establishment"], "reference": "CmRSAAAABMcYwWVmTr2ovk3uGW7Npo0S8o1hq_YiJkYTc3HA7nxCYJirFh7EEWZ-Cvjt0SJR8rm_NoHCtNDt4Zl59kmEs-yUM9Is6NF6IXw9ELdHCwoGAFGqQx9QIA0J6K3YhzvZEhCAph8t3Wcztn08aG5birhGGhTPuG2V4bWina8hprn8P6sJoVrFvg", "name": "Chemistry", "rating": 5, "id": "979d392b613c49fbb954ee393bff65bda5042b34", "job_title": "Adecco-USA-b5c07591", "place_id": "ChIJWxsq_4fSQIYRU9dRPmk8uIw", "address": "126 Vintage Park Blvd N, Houston, TX 77070, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.34630229999999, 29.72187359999999], "type": "Point"}, "properties": {"photos": [{"width": 4160, "height": 3120, "html_attributions": ["<a href=\"https://maps.google.com/maps/contrib/108375995272754268174/photos\">Nitish Thareja</a>"], "photo_reference": "CoQBdwAAAOJmJXtmr4YsmHxWRBfOiP-qap9YBKRb2XVkkSLZvU3mOyear4SWGLEUinhJ0dAX62aO26SbyWeOazc5PGE6DN-8B-fTLjZia9njIarG6JCikvX55PHRgxYCjxwA6f1adM_bXox3EL1bPaE6YgxvUyf0F6y9a4Jvr40VZ8ut7QZ7EhBWzJMHVP1WCvg1xaaBoiDCGhQgCx7AfrhWuexZwW11i61ViBm0-w"}], "types": ["point_of_interest", "establishment"], "reference": "CmRSAAAAcggtjMe9LtUqWvex_tZtBU9I2-_zUBC6nKlncFDhD5WNtwLuZPALCHs4Iue0g7480rWOhm4IUJNZOLcMtwFc5J-4DjisOKEdjxCDPNwzb71j4DmS66Y42Q7gT9FXkzAxEhDoyv1UorLZb2-bKdZuKq1ZGhTcpGF0Jm-2J22pbGbWe-GcpGApug", "name": "University of Houston Department of Chemistry", "rating": 5, "id": "baa83832f81135d0180e7850ce768a11f32e9df5", "job_title": "Adecco-USA-b5c07591", "place_id": "ChIJgRkjS1G-QIYRmcpaGaD6ZeY", "address": "3585 Cullen Blvd #112, Houston, TX 77004, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.4025992, 29.7198268], "type": "Point"}, "properties": {"photos": [], "types": ["point_of_interest", "establishment"], "reference": "CmRSAAAAs8_Ju5E7KbsCTs7ecXregb_kWlhOsMhV1tjtjV04f92tFcnuoNWkhOIB1GOe5GOaFBaZOMQ6tdLK_cKwUmzodTt4hTLvX8zyv5DmxNcnabOkZauvhqbR79VRYFQ5uEBYEhB9mZmTtMiIb9Mrd8OF_36PGhTiOsKnNl4prawF2aQtexyGtn-vJg", "name": "Rice University - Department of Chemistry", "rating": 3, "id": "1553681e69a2414f5cfa7551caa2102bc22268c1", "job_title": "Adecco-USA-b5c07591", "place_id": "ChIJL8yCnHzAQIYRZRcdAPRzhYI", "address": "6100 S Main St, Houston, TX 77005, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.4166517, 29.672442], "type": "Point"}, "properties": {"photos": [], "types": ["point_of_interest", "establishment"], "reference": "CmRSAAAADU1D7IBe1WlXzeyB-zNVXYDZ4EUtC88WlLf2Ni26TVXutqcTv1HzoDZqfaB4z0ZCqddIHBXq2TgVajuzI7Dxgs-eDrFO7GAUH1OzF5MyTVhyTCY3GnZ2yyzAxCMO4x6OEhAoUAuC0hHOzImi9BROCp5PGhSjR1Du0mveajwtHSFa3Fj05ynzqQ", "name": "Environmental Chemistry Inc", "rating": "NA", "id": "940f1e5d70276d8a5feaa5242d817666afa7f4b2", "job_title": "Adecco-USA-b5c07591", "place_id": "ChIJ7UpnzJjqQIYR2qG-Hcvp_YU", "address": "2525 W Bellfort St Ste 175, Houston, TX 77054, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.44932349999999, 29.7803218], "type": "Point"}, "properties": {"photos": [], "types": ["point_of_interest", "establishment"], "reference": "CmRSAAAAf7-dfno5r0iVSH5PkPO1NOKWRAI45W8S3hyWCPX6FaEFDVqBsJkvf9WEJ_iysKoqDPBDCGXkIR2VePK8ewLV-bHN74mxgSmu-tr-N-LFDPxP88ehP5liS-xh6q8XqnGbEhDFcmihTSS0O05IF1q4fIEPGhSyOSCmG-tbofB6BRgAg24yxV026A", "name": "Coastal Conservation Association-Tx", "rating": 3, "id": "7258b034e119f31e82320bca6e72781ee9f79d75", "job_title": "Raba--kistner", "place_id": "ChIJcekacM_GQIYRPzL13cgQrPk", "address": "6919 Portwest Dr #100, Houston, TX 77024, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.47039, 29.655454], "type": "Point"}, "properties": {"photos": [{"width": 5312, "height": 2988, "html_attributions": ["<a href=\"https://maps.google.com/maps/contrib/101184977609161362375/photos\">aug4</a>"], "photo_reference": "CoQBdwAAAGRHDYja8eMRkBjFpN2phX_mZgDgZ_NQVGm4nebfXQSD0KqoNp7WGDLgU6S_ovZdRQ982jJq4-PoBPkNHGujprdxuTgClufscQrXWPcnGqYjYwFqYxTRhn10eQkjjl0BE9pETcnEXtIHV3FmGECP8UdxgD4M-33K2debKJCdi2D3EhCnhrjCCYGD3fMnsEsP-_poGhQw5YzHUrRboQzS_zF7XxkjNM5mNw"}], "types": ["park", "point_of_interest", "establishment"], "reference": "CmRRAAAAZsAt7Ogrdwdx_Pi2IrkMhdh8wOXToMHt8KSkgzt1z4xLQdaVuW0_M5GQ2z6N-uT8NUcCUkOeojRaKgW1Rm9TQqWU5pO5xGgnhn8lOhztbLWFLPxi7ddhaI254p1AIfGyEhB9CivCMneDAVAOcUmgrWv9GhSlzRNVwTlYc9dYqmP0xAeP17nmhw", "name": "Willow Waterhole Greenspace", "rating": 4.3, "id": "0127506e8071350c2d48f0ca56e939045297a0f4", "job_title": "Raba--kistner", "place_id": "ChIJR6_2zTzqQIYRsA7wExgfDWs", "address": "S Willow Dr, Houston, TX 77035, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.4003322, 29.7388505], "type": "Point"}, "properties": {"photos": [{"width": 1136, "height": 640, "html_attributions": ["<a href=\"https://maps.google.com/maps/contrib/117056878997299689379/photos\">Marisol Brown</a>"], "photo_reference": "CoQBdwAAAGs374_JIHcbeYpGPO2nkbIAXzfxSSgHihiNVv983NioeAPBgCmG-UrUm23WWXx12xvVvfvCVJNoJa8S9UYNrg05KfNVNuUonfXXAELSjXSh53W6bDOx87B-tf8YWtFXa32_Zyhd7pUwjpZRAgXZFpBmpkagCOZ_972KScgd04prEhA3JlJXnnRTUl48R-8TSaSdGhTaeR1iefh4uRmMfWlJ3H6lJAGY1Q"}], "types": ["point_of_interest", "establishment"], "reference": "CmRRAAAASfOAQ4a1Th0i3IKBiE5XoSgrWWrTD4IjTA_ncVD1pVau0k47Wm1B7icQnCcXbHbL5mvAmPGUWySHR_0h6COk8QyEwu64LiV2U9Uyx_ucCfqS-7slyM9-Dl0zM8RFs23vEhBOl9z9s9clZ8hVtD56RxFCGhTPkogk5hHSEUHtmvgne6JInFXb3g", "name": "Masters Fine Art Conservation", "rating": 5, "id": "a462c2eef4e22ea319485ae7b84f3d20756cbdd1", "job_title": "Raba--kistner", "place_id": "ChIJp8u2bZvAQIYRbosnWz6cVmY", "address": "1612 W Alabama St, Houston, TX 77006, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.3876169, 29.794149], "type": "Point"}, "properties": {"photos": [], "types": ["art_gallery", "point_of_interest", "establishment"], "reference": "CmRRAAAAq5DG-izXMtERIL2rVooc9q0X0Bi8wUwRE9zkbSyZdbuURu9QKp3NARZ50YdOPf0uBnnFwN795rjIXzuLqkmZ0cBIOJyi2GBEc0U3PCK2bOqts_iE7EvhkdN-Sadiqf9dEhDCiXjX9wIifKBMo-KFTntsGhT6c_Rtm1YmtJrDA8MYDJeSacs6jQ", "name": "Whitten & Proctor Fine Art Conservation", "rating": "NA", "id": "883a8c5ef35ab28e1630235ad65a6b16506a67fa", "job_title": "Raba--kistner", "place_id": "ChIJ8YuXE6K4QIYRn1SF1hazFEw", "address": "1236 Studewood St, Houston, TX 77008, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.3858767, 29.7300997], "type": "Point"}, "properties": {"photos": [], "types": ["point_of_interest", "establishment"], "reference": "CmRSAAAALc3TGH0HhmdvnyuR1ftkOG0AotzTWXYZf6zZRoGKYvj0Ae2Mao52hadluC13qsmtAgJhPL49owa828oBNKcsM4AlIiD8BopGmgpBmaCfdroEVZdi-0d3Vhk7en__6USTEhBrrg71FYvLRoMJXa-NWh58GhQowuon7h0AaRmzchhYtrNwSA0NlA", "name": "St Mark Fine Arts Conservation", "rating": 5, "id": "ea2d4bac6d74716b33f456dff3aae0cc0b43cca3", "job_title": "Raba--kistner", "place_id": "ChIJKbDEoXm_QIYRcRFBlp0dE8A", "address": "4901 Main St, Houston, TX 77002, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.483218, 29.7482286], "type": "Point"}, "properties": {"photos": [], "types": ["point_of_interest", "establishment"], "reference": "CmRRAAAAc7lV3v1EGdX63t3XePFhdRst-Xpwt9Uop2SL79Z3ApJCJg-cYviuh9biV8UBWK49QeCn6est5_-Gk_d21Tfl4acmoEMSk13wBQ3XE7BDAUNYaOh1-cLtbGPgetuswaB8EhCUS7epS5bpXVzvDasDyYUtGhRsMICYc0xKwDij-eQg_Wprj0tjog", "name": "The Nature Conservancy", "rating": "NA", "id": "90af6fb9fb926dde9f7103577cebc4150bbb1dec", "job_title": "Raba--kistner", "place_id": "ChIJq-m4EX3AQIYRJkn4Lhccp2E", "address": "1800 Augusta Dr #240, Houston, TX 77057, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.42318089999999, 29.7345943], "type": "Point"}, "properties": {"photos": [{"width": 750, "height": 437, "html_attributions": ["<a href=\"https://maps.google.com/maps/contrib/106788706324997826205/photos\">Erika</a>"], "photo_reference": "CoQBdwAAANHQ4QFCUdiki2XB-6PEIBiQdGegvE6KTgDriMkJDJ-q_FvmrgI5uFwnfeXdaZZhQCw-mkjGTelSb_b_3KV4Y1jTDCk2KB_uCll7NTPwvhqsBnNougfY5ozZmIkrfv_xDBpek3na947ocd3U1WJcq21qj2dTgCIoPwkKZlyvbsUoEhBRHroMBF8iRVlfB1WDptA2GhSvQ0ngr4bnsxy0n_HpNuxkuKkmXg"}], "types": ["point_of_interest", "establishment"], "reference": "CmRRAAAAQ3GnKpoYnQCmlTa0KQvOF0ZokZ95PE_xYl4bEv32WRNUmJOSnD81twfERYrxyeeCECmTdP6Rj0yeikXNgAt5krK6WPUQqy550n6l2KGR8ON_E1BDy5ei7pO-GQoBZMN-EhAZl8TwYeNUkSDyI8CREK3TGhQA02y7x7SmQeymoj8EeBv1BBtC0Q", "name": "Student Conservation Association", "rating": "NA", "id": "1c5ea7722fc0d99e9f7dfca55f5d9078224d51d3", "job_title": "Raba--kistner", "place_id": "ChIJQcqBXfDAQIYRErawO-goGj4", "address": "2990 Richmond Ave Suite #400, Houston, TX 77098, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-96.038102, 30.055621], "type": "Point"}, "properties": {"photos": [{"width": 984, "height": 985, "html_attributions": ["<a href=\"https://maps.google.com/maps/contrib/110279808588468038448/photos\">Peckerwood Garden Conservation Foundation</a>"], "photo_reference": "CoQBdwAAADaL93Cvmd8UrDojUMONzbmFyxVMccslHj6xYCHAPuqHmzSaAT_LV5vUeB2xrhjWukg-PLFfVcC9L4IuY6P6lIyPZ3ejBan-amrHpo1Y7MIhU58VmYPLQUjsxyX_6s3-9t2-BwyH_I6s5u4Q1IUs5DlHMgSKYmG0buvMD4V9W3vDEhB3YdDGhR-1KJ9VRQrqlgcyGhTPJuuXyN9AHJMs-MZg7pLDCh72Rw"}], "types": ["park", "point_of_interest", "establishment"], "reference": "CmRRAAAAggpPliTvepmAez-QvUetnmMk1qFZHDR3I7Jsxcd9kpinZLdeKsRWaphpmOfap51qOlekA3fKVcZKRQ4GmJyzq7Y7WKAEyCT9czez6QO_Jbgavhz7fdUIGpIYD56Lbg5tEhD47JjJocEmgM5i1FvaERLBGhSHr-42EjFCI0KqiEFREGCZbpwuqw", "name": "Peckerwood Garden Conservation Foundation", "rating": "NA", "id": "e618a4c618cd67ce4f5fdc165f640220ab3b53b2", "job_title": "Raba--kistner", "place_id": "ChIJmUR7pvHKRoYRIIl0o73bPGE", "address": "20559 Fm 359 Rd, Pine Island, TX 77445, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.64386449999999, 29.7515036], "type": "Point"}, "properties": {"photos": [], "types": ["point_of_interest", "establishment"], "reference": "CmRRAAAAnlVNJPePOcvp7th4nMSHBuVnege_ZBwMaH2gJu1uZVxOyCqnDxxIP2caLbbXkHm9Z8tXzqyTcYvTd3rUkov4QNlLGTgirzDKTUQVDsxanara3QTlRJHP7-sIb0mdBLE2EhBcBN3C62vz0wCKW2RbFCzUGhSaxLGuDxTWjHJbuquoCAzlwECaLQ", "name": "H2O Conservation Technology", "rating": "NA", "id": "30c07988ef8dfc62dac712b9d587daa4a36f2539", "job_title": "Raba--kistner", "place_id": "ChIJIWZRKeHKQIYRXxta3wOMGGc", "address": "1725 Hwy 6, Houston, TX 77077, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.5705632, 29.7714443], "type": "Point"}, "properties": {"photos": [{"width": 3024, "height": 4032, "html_attributions": ["<a href=\"https://maps.google.com/maps/contrib/108143329814504597326/photos\">State from Jake farm</a>"], "photo_reference": "CoQBdwAAAGymFuf_XJm8zScuhYe0bh18D6rH7x1TTdA_aDJkdaY9AzobB-2WxL_2zp4s3ucOMhY7s6zI8Fqv1tmIrHLmsAflTCtEpR6TEO6edvGqu_SKRvjstku5R2Vs-d-Tw_tPFzzvfu8R01CZsBY8nsvKk-LsrhPRnxhUWDWTg8WUbKG1EhC964LDri0Q9raSePIPO2NtGhRQ87AV-Ykgtdgm8Jn-mp9_S-HVXw"}], "types": ["park", "point_of_interest", "establishment"], "reference": "CmRSAAAALgQ7IvxOss5sILc_qCM7DPSwEHUlpA2ERH1aOg6WqSpC8i5Gus72UmMGgqAP7k694d03GlWgsb3TjMz886pC7Ksce_yAEzWvLM3fGUabQ-sJr2hG1HHSC_p9QLZsu3FHEhAW--VSmapp53pLwmJdZSMzGhT1ooPBHqfQih8WdpVaiFpllIM7sw", "name": "Houston Audubon Society", "rating": 5, "id": "050a5458d86bdd1cee7b09678bd6256d0a20a73e", "job_title": "Raba--kistner", "place_id": "ChIJlQOxwVDbQIYR2uX_TZl0TYc", "address": "440 Wilchester Blvd, Houston, TX 77079, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.56820189999999, 29.770778], "type": "Point"}, "properties": {"photos": [{"width": 1800, "height": 1200, "html_attributions": ["<a href=\"https://maps.google.com/maps/contrib/108765250995932379967/photos\">Audubon Docent Guild</a>"], "photo_reference": "CoQBdwAAAGWuD4HBkhwl-F0Om3zun1wypGBYFltk4nloAlRP9bpRGkq6QEYoHIfu9gqj0-O7aKxRwLzslspEeeZw6ymCmjiCibGYMASkT6EaUdqJibT29emXJrJAjVSMSkpZraKNc1XKffJRWKY69b0t1NW_sXpNTyaCezkUEZ2_sEcJo2ynEhDuXJfTN4nt9oePdt-sc6IaGhRnSWysCd_TAJHRlf49q59NEBFOsA"}], "types": ["park", "point_of_interest", "establishment"], "reference": "CmRSAAAAYdEf36rxItv-9KDN_0L7MPcIeloUeyyilFqD3woxWIZgE-iq9j16On8iLT77_vUr-2DdTkafzjhDiAa58nXq_8rNdiB4PifloW0mhd9NIRQewoxfeQwbYaRXu6cYyTNNEhDJPDGtPnZ6t4QLChRjCL9KGhQUNdHrL1kgxQxfyYfdIcRCUiJOoA", "name": "Audubon Docent Guild", "rating": 5, "id": "7ddd5daf76cc4979e2ba6b062322d1c77d5d1c07", "job_title": "Raba--kistner", "place_id": "ChIJI9XyNFHbQIYRtwHb8EtTpeU", "address": "440 Wilchester Blvd, Houston, TX 77079, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.44932349999999, 29.7803218], "type": "Point"}, "properties": {"photos": [], "types": ["point_of_interest", "establishment"], "reference": "CmRSAAAAF9pVvyhHLHvXAAjglPtleD1g07DkazKZmjZZv_Iv4pAHy0wo1Sb3JRoq_G827o00PNapk9mN0MRjNfQFHIcLw53eA0O5CSa72t7ppOAmMEaJQKA6oUtoq5Ofax0s2ANIEhD9gy57uXDeAv_j36rdCeeyGhTCGGB9iaDqpE1HDrN0m4bNsQ4uWA", "name": "Coastal Conservation Association-Tx", "rating": 3, "id": "7258b034e119f31e82320bca6e72781ee9f79d75", "job_title": "Coca--cola-Refreshments", "place_id": "ChIJcekacM_GQIYRPzL13cgQrPk", "address": "6919 Portwest Dr #100, Houston, TX 77024, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.47039, 29.655454], "type": "Point"}, "properties": {"photos": [{"width": 5312, "height": 2988, "html_attributions": ["<a href=\"https://maps.google.com/maps/contrib/101184977609161362375/photos\">aug4</a>"], "photo_reference": "CoQBdwAAAOCiVPrFo-PswB8N88HDr6JD3q2bs0snxacW3V-0Hol1P0h5KuAkSsGozd9iDpSNoUlM4AZ8OjWhPih1qL8qITDBF4tdkZVG89KrP6HvMWF6ok39AZrAwLw-xi3Qswo4Yu7vgQhVtBOwoZRQc7d40ERq8NP2QQRyBK1rI0zYJGMdEhBb4ifphFCtJQapMAxOay__GhRX8_fRMs3pSeGvsdtV5nvJExvdKA"}], "types": ["park", "point_of_interest", "establishment"], "reference": "CmRRAAAA9ntCj-Br31anLVLK2Fl8jga9adxK_q0PPTqKCzulvkS9rJjGyiplkdqbB0qyEPBjQm6xGOstqVhfHFuj7GaES7_IdxiqpMFAYOmJjknat0cdrhm_ZTwjmDytZUy3wrx4EhDl1wjPkT7k8YtfFdJdq-bBGhTcoJ8DHAMOTjbgKEBwARmJSxvw4w", "name": "Willow Waterhole Greenspace", "rating": 4.3, "id": "0127506e8071350c2d48f0ca56e939045297a0f4", "job_title": "Coca--cola-Refreshments", "place_id": "ChIJR6_2zTzqQIYRsA7wExgfDWs", "address": "S Willow Dr, Houston, TX 77035, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.4003322, 29.7388505], "type": "Point"}, "properties": {"photos": [{"width": 1136, "height": 640, "html_attributions": ["<a href=\"https://maps.google.com/maps/contrib/117056878997299689379/photos\">Marisol Brown</a>"], "photo_reference": "CoQBdwAAABCU_ApugHYDAyyjchMU-tfxEl4c5HcOk-w_PicPTzDXR9zVYMTNsbpQgTYpNAmw32X4hDRR20XXpvdPEjpbGO6lifqOYCUPZwt3K79k1_kvNVKU4Coq9SOqPskudsQI6YtLqDUN8Eqb5wobZ8BYP-Q305Qc-_ehbIO0FP4NGb3sEhAIeakmCJ1ABBqXdR9UNAnIGhSz2oO4gWZd6_KJbbAnMm1syao6-Q"}], "types": ["point_of_interest", "establishment"], "reference": "CmRRAAAAwnTs29b5lTNhYi9muW3ngGPtMB0RpLuixfBBd_Aw2pDPZdTaNbTIuKSukGvy8BReQfFKO9_4m8WuJ99EOgDG8G_wpjrNZb3-3tI1HjWofWAuJN4kfLwUoheLCd5p19gYEhDUHUKm6P1DCagaLe-v9mH6GhQSYEYCOGDwM0rU8f92_GbNvcx0WQ", "name": "Masters Fine Art Conservation", "rating": 5, "id": "a462c2eef4e22ea319485ae7b84f3d20756cbdd1", "job_title": "Coca--cola-Refreshments", "place_id": "ChIJp8u2bZvAQIYRbosnWz6cVmY", "address": "1612 W Alabama St, Houston, TX 77006, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.3876169, 29.794149], "type": "Point"}, "properties": {"photos": [], "types": ["art_gallery", "point_of_interest", "establishment"], "reference": "CmRRAAAADOlafRQ5QbdIOr-GvNVZBdGI0HJBkDDTO8sVSAqIoYaTENGHXuhz0l5Ew7DDnf_b5xR2xxEj_xLULqXTCdsojr2GbUZt8lG723Xm8H26zfs3DZO2rqP3bpPYoCI6Ha9AEhC4pThLoyeYwN4679d7KfmIGhT-m2B4B0t3ywXU8rrss5KSz_oKwA", "name": "Whitten & Proctor Fine Art Conservation", "rating": "NA", "id": "883a8c5ef35ab28e1630235ad65a6b16506a67fa", "job_title": "Coca--cola-Refreshments", "place_id": "ChIJ8YuXE6K4QIYRn1SF1hazFEw", "address": "1236 Studewood St, Houston, TX 77008, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.3858767, 29.7300997], "type": "Point"}, "properties": {"photos": [], "types": ["point_of_interest", "establishment"], "reference": "CmRSAAAAG-9weqYvEUgErXt-gHxspuWcVQrQ3mDHiZOyg-5zWNlhUhnFxukMgn6LPq1GiR85GP2nUxLqe18Pkj9bT-qgJyu3HzWGBiRqFesM38UH2zlimZ7RnZ7NHhxt2ailybVvEhAb6dt-HqsgzJeJbI_vnFyDGhRPqR1L7JxESrniRU5yuL8tYGpcig", "name": "St Mark Fine Arts Conservation", "rating": 5, "id": "ea2d4bac6d74716b33f456dff3aae0cc0b43cca3", "job_title": "Coca--cola-Refreshments", "place_id": "ChIJKbDEoXm_QIYRcRFBlp0dE8A", "address": "4901 Main St, Houston, TX 77002, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.483218, 29.7482286], "type": "Point"}, "properties": {"photos": [], "types": ["point_of_interest", "establishment"], "reference": "CmRRAAAA-F4i0SqUFLPwypzdAb1Cw6ysB1TxAzGCH1Su5N4l3IO09Yvl8fHKtnkwLnEmRX5x29OhZg1gq32CIOwfCh-0Fx-JBhcj4B5vZ4s4SBS56vX381TEdrBZFQO2LUANYJhoEhAWsWp2zAzntK8O77lmcCLFGhRaCXQ9vxJhJOoLVnFVfIxMqe6kKw", "name": "The Nature Conservancy", "rating": "NA", "id": "90af6fb9fb926dde9f7103577cebc4150bbb1dec", "job_title": "Coca--cola-Refreshments", "place_id": "ChIJq-m4EX3AQIYRJkn4Lhccp2E", "address": "1800 Augusta Dr #240, Houston, TX 77057, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.42318089999999, 29.7345943], "type": "Point"}, "properties": {"photos": [{"width": 750, "height": 437, "html_attributions": ["<a href=\"https://maps.google.com/maps/contrib/106788706324997826205/photos\">Erika</a>"], "photo_reference": "CoQBdwAAAJWsffjbjlJpA07udIc8RK9AICKo9Bunq5JA6UPib2sH-wOeTK8cqvYEG7EgVovzk48IbR6u-jZuY7NcJ5uU4uyqvDECRyBOtK5x7d-VkFeRVgleFi2HqzTAP9LJOxUHA0WeUZaY9TQEoQMkpvJRfnuZhf4DkhyAIXaIyWeAUr9TEhAifyHp-roFbkrwswOB49H6GhQXeF4EdYlvqt7bZAnNKeL_vTzO4g"}], "types": ["point_of_interest", "establishment"], "reference": "CmRRAAAAoQcI0i7YRo1li9yaIthjWb0Nk_T1iXNAOipWsKfOXjiAYHKe33oXiy-G5CrkOVHahoYRgbmefF9Vq0inRJloDRPgXdJvaUTG8LkUBOvTOf5I98Tm1OGJLvoMPtQODHOYEhBGlJdBK7Uvam-ne7CfT41ZGhSsvSUiAZa6bsrmF0NYjBiO2LiUpw", "name": "Student Conservation Association", "rating": "NA", "id": "1c5ea7722fc0d99e9f7dfca55f5d9078224d51d3", "job_title": "Coca--cola-Refreshments", "place_id": "ChIJQcqBXfDAQIYRErawO-goGj4", "address": "2990 Richmond Ave Suite #400, Houston, TX 77098, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-96.038102, 30.055621], "type": "Point"}, "properties": {"photos": [{"width": 984, "height": 985, "html_attributions": ["<a href=\"https://maps.google.com/maps/contrib/110279808588468038448/photos\">Peckerwood Garden Conservation Foundation</a>"], "photo_reference": "CoQBdwAAALZmg118EIhlt3apnM85ZM5Ea5H2m8GT5xqFbLHmE-Wo8wlcb-wiL4MLmC6Iwp4Yin-z5qHTSYSIf2dbUYP4SCoguOZuMrV6ai42cUkYs3Zrv2shNFOWMhYYvPr_7bLuEgOGTQ-AVSilZq7Y-ejvm8OJieNfaKJwyKaj8O73c7VyEhBbMiwRObV-DzurLOun_54FGhT45V7E_AhkpcpZlv3VL6BIaf_0fw"}], "types": ["park", "point_of_interest", "establishment"], "reference": "CmRRAAAA8UUQ9QHUK17FqUCAQfWQJvPGY0fv1Yz2CMei3ENNKHGfAC0qufV6H_88eKmkdZ1NYiEh3pX9FLd4_3YBCJsCUR3ZT-3eSrfKgHK16kRcpYEmjq-0Z84CywTnDbIg6nVWEhCmFGAQ2KFPF2nEEkIvWInSGhQRlHr-NNJl3hlu6RmVMfXrS40pgQ", "name": "Peckerwood Garden Conservation Foundation", "rating": "NA", "id": "e618a4c618cd67ce4f5fdc165f640220ab3b53b2", "job_title": "Coca--cola-Refreshments", "place_id": "ChIJmUR7pvHKRoYRIIl0o73bPGE", "address": "20559 Fm 359 Rd, Pine Island, TX 77445, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.64386449999999, 29.7515036], "type": "Point"}, "properties": {"photos": [], "types": ["point_of_interest", "establishment"], "reference": "CmRRAAAAYF9T58MxZrWI_gzGM11gTa-yfu_Vgbfs5x3vzG0C2iB8jJGJbHG170l9Rp401ccYVz0MEr6aA3z-7-24W_xl8m6SVI_UB6F-t-qg3VZontOewPc2c9zG_y_90SGofBf1EhA_3PHjuxZFaccTz2zm0CuhGhTN6w6wLkBjij1f5z4ZXSUWDVPjVQ", "name": "H2O Conservation Technology", "rating": "NA", "id": "30c07988ef8dfc62dac712b9d587daa4a36f2539", "job_title": "Coca--cola-Refreshments", "place_id": "ChIJIWZRKeHKQIYRXxta3wOMGGc", "address": "1725 Hwy 6, Houston, TX 77077, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.5705632, 29.7714443], "type": "Point"}, "properties": {"photos": [{"width": 3024, "height": 4032, "html_attributions": ["<a href=\"https://maps.google.com/maps/contrib/108143329814504597326/photos\">State from Jake farm</a>"], "photo_reference": "CoQBdwAAALyIkBkXZUk7qDZhmuZSNUFBwGcGoNsHnyR7v1pyEgZN-ka2G5HAIePiDPHqNZif9Kqx4Y1YMOUT_7PqUlzc_F8Oe-3npApKeSCxpj3pk7TOYvvZ1Okx-BQ8ifKY6KEVPs2luAYH25WK_EdXmlEIFrtgnfilkMHp41IAUxg5Ro7pEhCm7TLVC_yqQTH-6YYQrWWOGhRliD6nBKkVl1BRsUVyV0_zkt_a2g"}], "types": ["park", "point_of_interest", "establishment"], "reference": "CmRSAAAA7OEGBAf3LJZWgQIFkuVrX21fRZ4KR0U2fPjrUQlRi5UBqTPC_mvQ7z-HK72yb3iCYVw3bersrMOPAKFnx6f-2D6bbZk7zJFDQEG4PVJfsLMNDWs8WByGmGOg61egFBn_EhA3_TKIedA1WrKkM3pz4G--GhQWQy60d8dqQzgS9GqVngr8hpyyYg", "name": "Houston Audubon Society", "rating": 5, "id": "050a5458d86bdd1cee7b09678bd6256d0a20a73e", "job_title": "Coca--cola-Refreshments", "place_id": "ChIJlQOxwVDbQIYR2uX_TZl0TYc", "address": "440 Wilchester Blvd, Houston, TX 77079, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.56820189999999, 29.770778], "type": "Point"}, "properties": {"photos": [{"width": 1800, "height": 1200, "html_attributions": ["<a href=\"https://maps.google.com/maps/contrib/108765250995932379967/photos\">Audubon Docent Guild</a>"], "photo_reference": "CoQBdwAAADX6ShmGxcvBk0OV3I18m3RI5nkuFbse4abpcBwg78snFzNqGADOcTtn5rtFWxRT0-nVaA1dRgXU89eHCFbgk1XMWfLirXI0b2XxByEqSFQsqVCq-qd6hJoXPct6L5zWbD234Pnc3eN_V5XQtCbncvLm3HvRqosyO__lJWz32BRwEhDr7mBFAl1j-JsJt7F8TIp0GhSYDjPaWQr7ymQR66_1oDphtwwNUA"}], "types": ["park", "point_of_interest", "establishment"], "reference": "CmRSAAAArvxE4nsob1EC72nSJe3fDEHM2ndrmnlQUtCCHHB0TJBYRTLRFECpSglSWe0BHEzQaQ-5F5iQgYpD_8i2O2XaailQ1ad7FmmtPdpR46vU9We7TYgdLLawJD1pyzzOjCWEEhB_Op3sJohWoYwI4PcaBy_oGhQ9UfxoHZouZF3Ob5pmd3JhCvlXTg", "name": "Audubon Docent Guild", "rating": 5, "id": "7ddd5daf76cc4979e2ba6b062322d1c77d5d1c07", "job_title": "Coca--cola-Refreshments", "place_id": "ChIJI9XyNFHbQIYRtwHb8EtTpeU", "address": "440 Wilchester Blvd, Houston, TX 77079, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.44932349999999, 29.7803218], "type": "Point"}, "properties": {"photos": [], "types": ["point_of_interest", "establishment"], "reference": "CmRSAAAAp30mACNkqz5-NkAJm2jl3MtxQaIgC8BtfoAtrZsxui_i8TUyDnjdlXOFNtttr4W1lUJKOefsNLsR4iKUvTF6JaMhxX5VGB0NnURNNNbf_dcXlo4D0FzaXmUOdLuYZoslEhA3is_Lk9PDFf-dV5Aafs6_GhRsH-78co0HxJ_LVTd28E1BUQ8-hw", "name": "Coastal Conservation Association-Tx", "rating": 3, "id": "7258b034e119f31e82320bca6e72781ee9f79d75", "job_title": "Dell", "place_id": "ChIJcekacM_GQIYRPzL13cgQrPk", "address": "6919 Portwest Dr #100, Houston, TX 77024, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.47039, 29.655454], "type": "Point"}, "properties": {"photos": [{"width": 5312, "height": 2988, "html_attributions": ["<a href=\"https://maps.google.com/maps/contrib/101184977609161362375/photos\">aug4</a>"], "photo_reference": "CoQBdwAAAPGdLvIIcu8KYpAKOOuHKM-FrOMrBYUswSIRjhYKxR1vl7GHkVx8Snx_euYFxXsbW2Pl1b-pAizO60qH4xrAV5FfKUc9RiJcUX488q8LBZwyRPqTRhFsLx5bKNyEMx1S4Dd52d6cO3nJlPpUQYawVO5lyd7j7TSy6-ufl6vUyQKfEhBqSuQpsoSlFEVZ_ZPGbqg-GhTi8piOjno0Fo6WakJjJRQH_kXLVg"}], "types": ["park", "point_of_interest", "establishment"], "reference": "CmRRAAAADvJL5Aza52u5BxY0HYZ_m9YPg852tqZT9_IF4ZmPottsJwCUz7FeTwWwnFtoEPqzY-ee4yCERTm0dlbQrCaSVpa9oDCwh8NtpkRQwdMYazjht_yrNJ89Y1DJvfnuXVgvEhDYSKzitAq4xayisn8P_xQtGhS2s2hZMulIsVJb0xalAgEu0I7yLQ", "name": "Willow Waterhole Greenspace", "rating": 4.3, "id": "0127506e8071350c2d48f0ca56e939045297a0f4", "job_title": "Dell", "place_id": "ChIJR6_2zTzqQIYRsA7wExgfDWs", "address": "S Willow Dr, Houston, TX 77035, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.4003322, 29.7388505], "type": "Point"}, "properties": {"photos": [{"width": 1136, "height": 640, "html_attributions": ["<a href=\"https://maps.google.com/maps/contrib/117056878997299689379/photos\">Marisol Brown</a>"], "photo_reference": "CoQBdwAAADMw0NpJV450vC6MGjAQQoal_kiGkynopNxXrXdgvrAlraQ0YLDEK6Gg3NA28qLg7ZkXl9NY-zfksQsbQ4wsq7UmqvCk9UGfD5gqHmha5jf9kxzzAnKcJ5np6fzYrOlWeTkczt6RqTUPsFVW8fM7bnM2n-rGHMUvCjHhRnTN6R_YEhAnPRluzYUlSeCps3Z41v6cGhTBiNcMTSfwaefD5igJ7FwPwMRbSA"}], "types": ["point_of_interest", "establishment"], "reference": "CmRRAAAAqaVztPO2hAehiQwzvVvm-BXwgt0yiOSSO87GlDNA-PsSNrCUFZd9e7y_DBfWgeHX-gE-U1oniI8FJR-VtJkNZZI7eYeZwhkRQMphUHGYxZRF3yLsnXnZjbB5rP8tOvsLEhBbdvxzKKcYGYH1ui7hVW16GhQyoACEEnO2eYvfu6JBUgwDSEAsXA", "name": "Masters Fine Art Conservation", "rating": 5, "id": "a462c2eef4e22ea319485ae7b84f3d20756cbdd1", "job_title": "Dell", "place_id": "ChIJp8u2bZvAQIYRbosnWz6cVmY", "address": "1612 W Alabama St, Houston, TX 77006, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.3876169, 29.794149], "type": "Point"}, "properties": {"photos": [], "types": ["art_gallery", "point_of_interest", "establishment"], "reference": "CmRRAAAAkHZuij04Jgnr6mV9uQTQpKK4JU9D8tnS8czqaudZNKsvvkWAyAS49zGVcoX6Mino4O3EDxya4ig5G9MEPj0LVAgtmuVpmBQPPP3-TK7WK92JKqmLUoEC575NJ5zOS_pWEhD9YXqljfj60PwY1fyM25-LGhTj8RfG5ZbUYcducxAa6Y0OXGxklQ", "name": "Whitten & Proctor Fine Art Conservation", "rating": "NA", "id": "883a8c5ef35ab28e1630235ad65a6b16506a67fa", "job_title": "Dell", "place_id": "ChIJ8YuXE6K4QIYRn1SF1hazFEw", "address": "1236 Studewood St, Houston, TX 77008, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.3858767, 29.7300997], "type": "Point"}, "properties": {"photos": [], "types": ["point_of_interest", "establishment"], "reference": "CmRSAAAAara4B9n1QlViSwuuVHowrCITvgaNykq2VRhJzt4q1PqLuw6WxScRjuCvPsAZx2VnFFoFDzVl7uU1lLEK0hm4w86R4WkxapHn3H0OAuHh1RyqAV1bfz_0Db2gzL2HCBDjEhAI4ybJ8g0cwwWWYIXNeBp8GhShuKlqz8Bp6xmmuTuKRLCw_5ttxg", "name": "St Mark Fine Arts Conservation", "rating": 5, "id": "ea2d4bac6d74716b33f456dff3aae0cc0b43cca3", "job_title": "Dell", "place_id": "ChIJKbDEoXm_QIYRcRFBlp0dE8A", "address": "4901 Main St, Houston, TX 77002, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.483218, 29.7482286], "type": "Point"}, "properties": {"photos": [], "types": ["point_of_interest", "establishment"], "reference": "CmRRAAAAcdoYbsHsJ2wNtG-V4ibXSOTPphmw6_zPQPhCmtEtY_laYemr_n1chYX0zZu9qWRKEEZVr7k-tFF5S_eVa91p33uGIq-4fC4gdkkvtTRkgLvDMl41MAYQQsYjaaQXwg1EEhA1zYY2aWymvk4VIEjoNbR3GhQ8EvhPQqTs1URSZwtF0DBusqtgAw", "name": "The Nature Conservancy", "rating": "NA", "id": "90af6fb9fb926dde9f7103577cebc4150bbb1dec", "job_title": "Dell", "place_id": "ChIJq-m4EX3AQIYRJkn4Lhccp2E", "address": "1800 Augusta Dr #240, Houston, TX 77057, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.42318089999999, 29.7345943], "type": "Point"}, "properties": {"photos": [{"width": 750, "height": 437, "html_attributions": ["<a href=\"https://maps.google.com/maps/contrib/106788706324997826205/photos\">Erika</a>"], "photo_reference": "CoQBdwAAAEl4tB6yfuWXoo1wC-vYlIxov03lMFxx5aRXDPg8P90gcox96XM7V_OfEC_Rew6wJqpNqU_t6KpT3cuuMMEOtoaUGb8c8TEl1O6YQxAbmH2IHnew2VzmKQeBEwLz2scIgInwBNbM-z9qqxUR5hulRh3tiq_Dwcds-7YpwnN-IL-KEhDC4u7Y5g7vb8NEIvm8bQuiGhQv56vSp3v9jEvOwGr5m-tr2cbhrw"}], "types": ["point_of_interest", "establishment"], "reference": "CmRRAAAANc4_BSjXQjFPok8hyu1OMc2_DaDdGODovps48xH9lC6bnRiS6zjaPSvUGXrEIGI1Qwg22I4m8FkijBglqvBBYoRit46HYwNrCQ9Zo0RB0KrMftjz-82AFvSRG32g8HPfEhAxSYtgAFs8g-tn8kEo9n7sGhSXez1m-AIcA2flbbmNj1BbL5VuPA", "name": "Student Conservation Association", "rating": "NA", "id": "1c5ea7722fc0d99e9f7dfca55f5d9078224d51d3", "job_title": "Dell", "place_id": "ChIJQcqBXfDAQIYRErawO-goGj4", "address": "2990 Richmond Ave Suite #400, Houston, TX 77098, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-96.038102, 30.055621], "type": "Point"}, "properties": {"photos": [{"width": 984, "height": 985, "html_attributions": ["<a href=\"https://maps.google.com/maps/contrib/110279808588468038448/photos\">Peckerwood Garden Conservation Foundation</a>"], "photo_reference": "CoQBdwAAAIADDJtiJ8h5tNKK0XcBtzQ9ah5L2VqNwPP2WjCxILB1k8zezp2NVn0RqBUebxIZpY3XZKuPv_WbkLrf5U0Hy5jnjAtB3uBX6XKtkT1voSzPQ-_50cSvlPoiv3Eh2Fw7yDf0JtW7g0S0LK-drF5qsLW2otsQsxbRxg8CC2hULDxJEhCl2SHttVaEybRSJX5rb_PBGhQ6VYLwUW8tzexkkSYK43eeA_Ynng"}], "types": ["park", "point_of_interest", "establishment"], "reference": "CmRRAAAAO_uD5_uWsMj9mnzFVqTKf7UlA0mXLvGrC2n-Il8GAG_IPL3M2eh9gZHnuDpKer7ZzTzx2Txhp0FZ5wNkOTGGdqALmNbgNvrfO-AbvBBmwnTCjGwsdpJPw6PJVT3NPVjGEhBqJXIV4JttaeOgMvXmjmKpGhRApK655ZHJckzkW-FVZJrRX91P9w", "name": "Peckerwood Garden Conservation Foundation", "rating": "NA", "id": "e618a4c618cd67ce4f5fdc165f640220ab3b53b2", "job_title": "Dell", "place_id": "ChIJmUR7pvHKRoYRIIl0o73bPGE", "address": "20559 Fm 359 Rd, Pine Island, TX 77445, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.64386449999999, 29.7515036], "type": "Point"}, "properties": {"photos": [], "types": ["point_of_interest", "establishment"], "reference": "CmRRAAAA4FywEIdszrg0Wba3N1mjEJ108PJOHptCNymg6eKmJE_abyG6t1_HEQYeFEElRMoCLhVt_Yh-li4U3hYy7WfuRsfk2NEKA5J0IvvsbQML8aGRYYuIIixrrMaq29l3efq2EhAIQ1nOvPi7rpYuHFxvprXFGhSStOjRTdZ2KKaBSTSgMcR10p7x8g", "name": "H2O Conservation Technology", "rating": "NA", "id": "30c07988ef8dfc62dac712b9d587daa4a36f2539", "job_title": "Dell", "place_id": "ChIJIWZRKeHKQIYRXxta3wOMGGc", "address": "1725 Hwy 6, Houston, TX 77077, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.5705632, 29.7714443], "type": "Point"}, "properties": {"photos": [{"width": 3024, "height": 4032, "html_attributions": ["<a href=\"https://maps.google.com/maps/contrib/108143329814504597326/photos\">State from Jake farm</a>"], "photo_reference": "CoQBdwAAABiZeBv2sB2gc7pudoyd26VzL5R0qBtUFbLr4mePowMhM8s44qV4sNwxdgKtAO7QX4-D8kxHx6f0ovG0gYSttS4C8gOf7unzFXDvVM2cAyeobrOMnbF6FMZ3FHkgmf593-PTgHhDXmwajIo6_wDKH1ApDIYTWz2lSC1IB59oLbb9EhBTiYCD91tqAXFQXx6HY0AGGhSoCS3czdtir-MZ3d6gBltjonhqJg"}], "types": ["park", "point_of_interest", "establishment"], "reference": "CmRSAAAA_YX0_rbLPxwhmbybuXbH7pyItUY4gVpEtjYMZa3iofDKR6mdxt7Nb4fCmM5rzQBE5ft_qZ4Qcf9XRMsHTazXH_eSDKqPmzwVUmaK4ak3xDATivyO2NolnIlW3nV6Owj2EhDXM5_hBZWLfPwQXmdW76ZxGhS8NMmP8CO9ZOHj2D6aqI4SqOrzLg", "name": "Houston Audubon Society", "rating": 5, "id": "050a5458d86bdd1cee7b09678bd6256d0a20a73e", "job_title": "Dell", "place_id": "ChIJlQOxwVDbQIYR2uX_TZl0TYc", "address": "440 Wilchester Blvd, Houston, TX 77079, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.56820189999999, 29.770778], "type": "Point"}, "properties": {"photos": [{"width": 1800, "height": 1200, "html_attributions": ["<a href=\"https://maps.google.com/maps/contrib/108765250995932379967/photos\">Audubon Docent Guild</a>"], "photo_reference": "CoQBdwAAAHeL-0P-BaYXtwifgIpVLE4p6W7UMwfvhmk8xbpnGsxz-6ryAjMI3vloUZ-_FATjB7NdOagIq3uG_YGqezmJsfmv8t-aYUAV9rPL7lmpDmtAPIjgMv3k8dPLAw0SWcPv69Xn0fOqDoYiEzm34N7QXj56zr4HxcfdXuna7JEYby5bEhANLaWVOdkefbeh9AZnXOYRGhTY8SZJWq71VPQzfv47fzAN5YQW6w"}], "types": ["park", "point_of_interest", "establishment"], "reference": "CmRSAAAAkLpFH7b9k59qqBfoYQhozn5MyGdN5IWNszOTu9FlxVUmAAMGL1nYfIlXYXnG6xgnffGHg7cSCRVMwvEUqIpA1dhvXiflToqU08rn9lLi59APHwBvZMaICGW_8uwbgWKCEhDUARMeVTOE15ME-EQTpWPYGhTGpiHzpYqvqJW7VcsqurTXEaECwg", "name": "Audubon Docent Guild", "rating": 5, "id": "7ddd5daf76cc4979e2ba6b062322d1c77d5d1c07", "job_title": "Dell", "place_id": "ChIJI9XyNFHbQIYRtwHb8EtTpeU", "address": "440 Wilchester Blvd, Houston, TX 77079, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.44932349999999, 29.7803218], "type": "Point"}, "properties": {"photos": [], "types": ["point_of_interest", "establishment"], "reference": "CmRSAAAAJoOWGcC2PvXcl8rmwrNYRy9T7C-uqwWXjnSkLJiqMGe5k6MbCkNmxGgIWP8lxkgkDibOLNoIHWxqFGy8GcSCcR7jAd2ZpS-K8uTfzUE3RhUthkWZkI8wqodesOWEw_pLEhA1UZU4yCgnLQhKHi4DcjJUGhRZ8LPZS-3FKymFuDbgy9QQawErHw", "name": "Coastal Conservation Association-Tx", "rating": 3, "id": "7258b034e119f31e82320bca6e72781ee9f79d75", "job_title": "Home-Health-Care-Network-1", "place_id": "ChIJcekacM_GQIYRPzL13cgQrPk", "address": "6919 Portwest Dr #100, Houston, TX 77024, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.47039, 29.655454], "type": "Point"}, "properties": {"photos": [{"width": 5312, "height": 2988, "html_attributions": ["<a href=\"https://maps.google.com/maps/contrib/101184977609161362375/photos\">aug4</a>"], "photo_reference": "CoQBdwAAAM79hpIwjTCDXk78W-te_m-KxjKrGu3yyyFSf1tljfLETuwllsLFWfbkrc7-5JY4w0T_hoU7uNro5XNXxRDFHxsm42JPs6QC-La4vYogm-wAqSiMXiYIQmw4PKHkP56-OcTIq8mEsHPvY-pK4d_wy7oKQxR-2YL6A41OCTzDWH0bEhB9bRxgP2nBcZ8zw8b-ehWIGhSJvF1ylTZqQYzlPzNvbVnW7vrhPw"}], "types": ["park", "point_of_interest", "establishment"], "reference": "CmRRAAAA8kx2X9VbBkzcI6yz6uRwmuWPRt2XW7hdM6icUgKpfoihs9FHkRuX0Xp3asOrl2QAPH7Xe2ZAiliYpjqfZmPQjwn4LCSKj6wNhD9wyNwyNk1EtjwbgpwXaBF8BMgcxIzzEhBIWvJihONlPcFOVWqPio92GhQvoIVY6meXxgcRJzDkwFRVe804gA", "name": "Willow Waterhole Greenspace", "rating": 4.3, "id": "0127506e8071350c2d48f0ca56e939045297a0f4", "job_title": "Home-Health-Care-Network-1", "place_id": "ChIJR6_2zTzqQIYRsA7wExgfDWs", "address": "S Willow Dr, Houston, TX 77035, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.4003322, 29.7388505], "type": "Point"}, "properties": {"photos": [{"width": 1136, "height": 640, "html_attributions": ["<a href=\"https://maps.google.com/maps/contrib/117056878997299689379/photos\">Marisol Brown</a>"], "photo_reference": "CoQBdwAAAPNRKcUdRJO7KGpQbaRlpE98doBFIOryL640kapG4_nLGBN2I2ja4AbNAoxno_2sSvJnfL3Gpvfu--fx-US0uDVv48X92eW3OZVVPw1pLoQCiUp65gHB-Hp-XU28AcpsK8Jm3kjWOYPJPqKzf2slFzbcm9A-GYt_qQmoBL7quyXkEhDGNI04qeYsleK-72jk1v67GhQRKer1ExkmARTMimqq94-OROPxgA"}], "types": ["point_of_interest", "establishment"], "reference": "CmRRAAAAvDCjsgZjO_9kUOTd-ldFbfNbseFucu8cVxPfOhaWDQugNGfibxSG3-QOFPF6ODgOXsRs_Bfdy1gkAesDIdO98NGOLwEh3P_MoybjvxLYZR6hrJOk8gr5iyY1c8lR-bXjEhAJEE6ijpRHgSLi6E3CDPSTGhQimo-IyngA40G54VKnAp4rUQOFfg", "name": "Masters Fine Art Conservation", "rating": 5, "id": "a462c2eef4e22ea319485ae7b84f3d20756cbdd1", "job_title": "Home-Health-Care-Network-1", "place_id": "ChIJp8u2bZvAQIYRbosnWz6cVmY", "address": "1612 W Alabama St, Houston, TX 77006, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.3876169, 29.794149], "type": "Point"}, "properties": {"photos": [], "types": ["art_gallery", "point_of_interest", "establishment"], "reference": "CmRRAAAAC_Nzc_OYkN41LHPfYin39IMQpMZOh952qV7N9EvdzK4MqwN79EAQ_K5DMsmcWZB-MRFXCX4gshIG1lL2q8Ld6ZPTJdnzapPRA80QaXCfQ4ZaRsD_epjzfU1MpqPId2peEhBsxcMKWNZLClDNQo3_eX4KGhRGhxOSXnmEGUKwVUmuawDiRAv1aw", "name": "Whitten & Proctor Fine Art Conservation", "rating": "NA", "id": "883a8c5ef35ab28e1630235ad65a6b16506a67fa", "job_title": "Home-Health-Care-Network-1", "place_id": "ChIJ8YuXE6K4QIYRn1SF1hazFEw", "address": "1236 Studewood St, Houston, TX 77008, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.3858767, 29.7300997], "type": "Point"}, "properties": {"photos": [], "types": ["point_of_interest", "establishment"], "reference": "CmRSAAAARNirGIFafG8RxCI7JArbVpjbwZ-9IWqoVwhHIFN8XGZ1lsvdp0nE0CWX4hEF3BDFI6uAI1cizFHznAYiAHVowiv2ygZdD_r1ubsiaTWNkJiHcUj3vsxZdXVcORAdgwz-EhB7iJw5mONCPD0IvpNz9Ju4GhSWaq3glklTv3lyyR075-Hu_JVhtw", "name": "St Mark Fine Arts Conservation", "rating": 5, "id": "ea2d4bac6d74716b33f456dff3aae0cc0b43cca3", "job_title": "Home-Health-Care-Network-1", "place_id": "ChIJKbDEoXm_QIYRcRFBlp0dE8A", "address": "4901 Main St, Houston, TX 77002, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.483218, 29.7482286], "type": "Point"}, "properties": {"photos": [], "types": ["point_of_interest", "establishment"], "reference": "CmRRAAAAUs5RfQuMRkKp3ylsLj3buMN3tcqA5hIXsFTOXoweeVKPvivwrhdedLsmNYaSHFyT5tohTAxc1AJzOQfVk74_YIWiWgNMkCkBUvruAqTZdAp61O7_S3ZrdLNUcMT-OJtPEhBP7Xft43Dm3faRgr3wCAaqGhSeXmv7SXaYwUV9_QuuzLkVTF2ZUQ", "name": "The Nature Conservancy", "rating": "NA", "id": "90af6fb9fb926dde9f7103577cebc4150bbb1dec", "job_title": "Home-Health-Care-Network-1", "place_id": "ChIJq-m4EX3AQIYRJkn4Lhccp2E", "address": "1800 Augusta Dr #240, Houston, TX 77057, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.42318089999999, 29.7345943], "type": "Point"}, "properties": {"photos": [{"width": 750, "height": 437, "html_attributions": ["<a href=\"https://maps.google.com/maps/contrib/106788706324997826205/photos\">Erika</a>"], "photo_reference": "CoQBdwAAAB4VgySD8ouJVVzs4Hq7Z-YSS372S1AgC8iAG4GoeRSVFHU__6xgCmXScfC5mjDeMH41useqGzJYlwVaEDiyMV51MfZu0TydjBys-c8OqC7FUNx1vpx8pm59qnloOfPRlosaPcb0sAZTXcz_mYHoYuf1rlWuDOi6OnmY6rrUT2XCEhDBLTbyNLob4Uo79OHg90iDGhQmtHSNGXk0BkX8I_UdAP47iGPWsQ"}], "types": ["point_of_interest", "establishment"], "reference": "CmRRAAAA19wHBUKb4HUOl0KRzgIVSyDmpqh_a8BhdUDdM_IlQuZeJSH50DEtZ3sNxMbTOv79cAskpyrCviEiZKn-XhaByswAgwaeSmMCE20IKVnNZypxdQAZRh_uRAugnzKqLbIQEhD4jBv_NvA2-wv7RB5blAikGhT3LvuTcFxE-oEp4NZ90SdjldFsdQ", "name": "Student Conservation Association", "rating": "NA", "id": "1c5ea7722fc0d99e9f7dfca55f5d9078224d51d3", "job_title": "Home-Health-Care-Network-1", "place_id": "ChIJQcqBXfDAQIYRErawO-goGj4", "address": "2990 Richmond Ave Suite #400, Houston, TX 77098, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-96.038102, 30.055621], "type": "Point"}, "properties": {"photos": [{"width": 984, "height": 985, "html_attributions": ["<a href=\"https://maps.google.com/maps/contrib/110279808588468038448/photos\">Peckerwood Garden Conservation Foundation</a>"], "photo_reference": "CoQBdwAAALmSaJ3G7n1E3KbGU7SZsR77jzxbDJ4sENkHletRUrlx1Kds_EoxnIPgFHDXG_Qy6dIkbt4hRtk437VXHWWG_nCloCI8N-XoDkUiuMhd6CvXEmeeH9G9eI0AumTUvx9NoIgEX6OxbD0ucqT6vQnCRWKpwFQM81VFBBPOSCyXbY8qEhBhquYBKgK1N0gX3KWlt12vGhSgrXojVvBIaUUoCITEa2mJwn1QKw"}], "types": ["park", "point_of_interest", "establishment"], "reference": "CmRRAAAAUAlNN9qXnI7JEaYRiaZhnQYXcqg5Xg1MyGIEcoDpbyZCVNfrMUbm17VUVX32-xY7RqKcv8LZHOIDCKlTrzd2tcTyliM1e9gC4qluEDgZ8VdS490hAWdh2_JslfxDC_1xEhCPdQiIg4im_LaMxO37OhOmGhRf0zXWBqCih1vrUDqev2e1YKb_AA", "name": "Peckerwood Garden Conservation Foundation", "rating": "NA", "id": "e618a4c618cd67ce4f5fdc165f640220ab3b53b2", "job_title": "Home-Health-Care-Network-1", "place_id": "ChIJmUR7pvHKRoYRIIl0o73bPGE", "address": "20559 Fm 359 Rd, Pine Island, TX 77445, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.64386449999999, 29.7515036], "type": "Point"}, "properties": {"photos": [], "types": ["point_of_interest", "establishment"], "reference": "CmRRAAAAJiiZWavKh40D5iSd5G8kkJk9HvIKuwQoyySHzqxsxLM6IVRLEhbcGpeaZRC4_qV6B4Yz0XQZ_V8Dzfc-UO_0l33V2soqBlIjaV1ZqoVei4KJ47wg-RDfa-mv_DeSHybzEhCWxBsgh3yt-7kiI8fg67LsGhRE5jDUfttVp04tbMGAmLq26BbQoQ", "name": "H2O Conservation Technology", "rating": "NA", "id": "30c07988ef8dfc62dac712b9d587daa4a36f2539", "job_title": "Home-Health-Care-Network-1", "place_id": "ChIJIWZRKeHKQIYRXxta3wOMGGc", "address": "1725 Hwy 6, Houston, TX 77077, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.5705632, 29.7714443], "type": "Point"}, "properties": {"photos": [{"width": 3024, "height": 4032, "html_attributions": ["<a href=\"https://maps.google.com/maps/contrib/108143329814504597326/photos\">State from Jake farm</a>"], "photo_reference": "CoQBdwAAADxPsRMqJj36cmEei9ADK0cmi0NF3JJ7LOYM3eB4nG8wRcwnGfgga89ZoR4A9ciaiVeG6JF4H-mTvMbvZMQuedgJTi1qM4-D98A3Hvus2rjZcQeIUk5oAadM1KTaNknRcGS8u6-k2Oz4wnjRRlSHJiX6fq1b0JL-8oQ6eMeTPjcFEhCu0oAAikI8_axGsqJjXSiFGhRjK8IvOksTlMOf5rULCjpI-TUzHA"}], "types": ["park", "point_of_interest", "establishment"], "reference": "CmRSAAAAwJ8qOoXt1aqoc29DGhiU-ukZu7QYVmUWFBIvsfqZQAWRNNs9uinCNLGiR2je_YbgVn2ld1MfabwZSGcg94sOOkJgVM2_jx3RhsxcSVJ_XC3Xhk5dB0hTrG2rCQY6rYw0EhAMqf0LMlCSfYGEwt4J3OLSGhTwzErGqeFK8GiZpTjm7Tuz1-O_NA", "name": "Houston Audubon Society", "rating": 5, "id": "050a5458d86bdd1cee7b09678bd6256d0a20a73e", "job_title": "Home-Health-Care-Network-1", "place_id": "ChIJlQOxwVDbQIYR2uX_TZl0TYc", "address": "440 Wilchester Blvd, Houston, TX 77079, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.56820189999999, 29.770778], "type": "Point"}, "properties": {"photos": [{"width": 1800, "height": 1200, "html_attributions": ["<a href=\"https://maps.google.com/maps/contrib/108765250995932379967/photos\">Audubon Docent Guild</a>"], "photo_reference": "CoQBdwAAABAXjfwVa-e_AU9sc8xVghyGx5UQwrAyT7WtVK1qCSvYrCkt9QLFTt1Tm6DOWPpJUHLOBL1xvEVVwneAIpHKu43FdL3SkK7I0nBHCS5lJVeO4KwSvC5WYZ_kRUONyi3Egx3dxCcRs3Wzz01sy6tPXjJtaP94nsvf33ekHf1mYp8jEhDSWjG38T32XQxycwBxXoNKGhRYgLUaVKeMn6srWXg9VffH-TBAeA"}], "types": ["park", "point_of_interest", "establishment"], "reference": "CmRSAAAASwcfj8IdPtbbNihakrurJc2LVQNjYm9wtDqaOiKUDyPkmZaD67zzeQIWabGLxnP4VboyL8YIpxaQB7KX7mXjbZSGtCNN9p7fKk1zbzkUXqdCjB-4fJyZ-ukRKuWo0mtoEhBpLEGAuXYMrv0JFaSYn23JGhR3Yz4k-8q8KRll7pbr7Di-TGdkTw", "name": "Audubon Docent Guild", "rating": 5, "id": "7ddd5daf76cc4979e2ba6b062322d1c77d5d1c07", "job_title": "Home-Health-Care-Network-1", "place_id": "ChIJI9XyNFHbQIYRtwHb8EtTpeU", "address": "440 Wilchester Blvd, Houston, TX 77079, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.44932349999999, 29.7803218], "type": "Point"}, "properties": {"photos": [], "types": ["point_of_interest", "establishment"], "reference": "CmRSAAAAxVA7NoSrJbTzNWWR9CurfME3uz6O_cRaskR5c6G6nE9iaw6uUaGMwVF64tghTWEEdP9PHlD4kYJPy6RlzAMtAwytprZFBvZAVsZe-ShNofKU7xvWca2fjy8jjOpt4genEhAz7YFfskvOyREkk615_W3OGhQ9l91hAAgfzrHHo5nhSjsblSUMbQ", "name": "Coastal Conservation Association-Tx", "rating": 3, "id": "7258b034e119f31e82320bca6e72781ee9f79d75", "job_title": "University-of-Houston", "place_id": "ChIJcekacM_GQIYRPzL13cgQrPk", "address": "6919 Portwest Dr #100, Houston, TX 77024, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.47039, 29.655454], "type": "Point"}, "properties": {"photos": [{"width": 5312, "height": 2988, "html_attributions": ["<a href=\"https://maps.google.com/maps/contrib/101184977609161362375/photos\">aug4</a>"], "photo_reference": "CoQBdwAAAK61-PlEgXbXFGyF2Xoo61wTtg7cGH57IraX4YHjjLrH2CXZbKIlS6PRkKLBeOgVn8sI1_jiZzyOA6uWER4oXe92OBb7r84AfUSyujF99e33ucaGqxL3yxTmPc9ugT6XBH810XawcqUe490_YR4509GfSp7L79r_EDePMCdgKkvgEhAEuse2z4LyC3bEX5CaufW8GhSACM9mjnfbeYHYOqxaBnql_4DitQ"}], "types": ["park", "point_of_interest", "establishment"], "reference": "CmRRAAAAFSm9P_6K0RtgP5hrJeFkbEkxYwhIV8AstGhP_9dbuefiA6HCIWbc4jnc3ziFNi79IJzwCrWY1iFT0PlBLL8SHUD3VAppFI7DHEKK64eo_lyaYQQrAVvJ5_6HHC9Ma0A7EhAxyzIrtEqFvD-UeKE76xeIGhSlQG98FgOZozb0F8zjSZbRXYmkow", "name": "Willow Waterhole Greenspace", "rating": 4.3, "id": "0127506e8071350c2d48f0ca56e939045297a0f4", "job_title": "University-of-Houston", "place_id": "ChIJR6_2zTzqQIYRsA7wExgfDWs", "address": "S Willow Dr, Houston, TX 77035, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.4003322, 29.7388505], "type": "Point"}, "properties": {"photos": [{"width": 1136, "height": 640, "html_attributions": ["<a href=\"https://maps.google.com/maps/contrib/117056878997299689379/photos\">Marisol Brown</a>"], "photo_reference": "CoQBdwAAAPX_wUVrV4O6NXKtQa3bIuywT8SZV-hreWXn4mYwHOQzViCpZ5KOwKUmXP3O6JUOnw2VOuvllle3FvKLPI5tJS_Oo-1QsEFQzdmo6MjVLmOc5yX5D8MGcg332hXI9ucesWFrtOwI_ofdohem6j5vxSpElSp3p9FAR09E4wyRPoXxEhA9ppQkj5augRTS5z9iXSfRGhRD5aSiPrRTMg1XVaTxC3Xlh313_g"}], "types": ["point_of_interest", "establishment"], "reference": "CmRRAAAAo4I5YBREVexVv5X7aoplnGSYmSuV86IAwKoUaZll6OXTJ_5ZTuQDgG95Be4dLkJyHXzn5dqB6_LPPZKV89YDvVHxbcbLI-ksKMOxJd1T0ud9yBAtLykhAA3ieZ1jlfCcEhCkvDt2MNcoftdBZNrLrrLJGhRJJqxP_Y3pyzw04msO_KvRcWQITQ", "name": "Masters Fine Art Conservation", "rating": 5, "id": "a462c2eef4e22ea319485ae7b84f3d20756cbdd1", "job_title": "University-of-Houston", "place_id": "ChIJp8u2bZvAQIYRbosnWz6cVmY", "address": "1612 W Alabama St, Houston, TX 77006, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.3876169, 29.794149], "type": "Point"}, "properties": {"photos": [], "types": ["art_gallery", "point_of_interest", "establishment"], "reference": "CmRRAAAAPSLH2NgfGry84sjbsOYJPK95XCE5p-63L9ji8glBrsFa6c6MGkyUvS9VNLX2HwZFu3ZgBKazIGLNbvzBefG56I-FmgxIm2XWPN-ep0n2F49Lr6oCbW1MSsRCAWb3oys-EhA7QSJUPccz-x3KiZL7jfBDGhTKYB2w2HNrLs4sDh1fax0Bup7E7g", "name": "Whitten & Proctor Fine Art Conservation", "rating": "NA", "id": "883a8c5ef35ab28e1630235ad65a6b16506a67fa", "job_title": "University-of-Houston", "place_id": "ChIJ8YuXE6K4QIYRn1SF1hazFEw", "address": "1236 Studewood St, Houston, TX 77008, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.3858767, 29.7300997], "type": "Point"}, "properties": {"photos": [], "types": ["point_of_interest", "establishment"], "reference": "CmRSAAAAtcxJGXuI0sCMs4zpJFuul4nYMVcrJmDJqssi8z5WZq-PRAv1hur6wRxo6iIxWuvWVKzSaNoNGyKVEemd6Cp4ujXIzNYxzcAJEE8L_j-6pXoZ0viaMBrSMlDDWhq5Gbz1EhDGoDJ3vkqO7nJZKuEBCAAwGhSOQgwWzixq1sGtckCJRC7EALBEdg", "name": "St Mark Fine Arts Conservation", "rating": 5, "id": "ea2d4bac6d74716b33f456dff3aae0cc0b43cca3", "job_title": "University-of-Houston", "place_id": "ChIJKbDEoXm_QIYRcRFBlp0dE8A", "address": "4901 Main St, Houston, TX 77002, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.483218, 29.7482286], "type": "Point"}, "properties": {"photos": [], "types": ["point_of_interest", "establishment"], "reference": "CmRRAAAAMtbyL64QC_DvSk6pMa2Ug6MGg372LcMhXr6borTX-X2Ca4nozuQv9aZXwg4opQE-UuM4gjAi0gV7JE4VgAK-JHBiatuWE4IiC3ZRb0fko3RDh-84GJ6ppAxvmkMiaLJdEhAIJGTBk2GV2OmEdqaBEMUkGhSICFaccJKHNFGlg0mnTVFLOfchtQ", "name": "The Nature Conservancy", "rating": "NA", "id": "90af6fb9fb926dde9f7103577cebc4150bbb1dec", "job_title": "University-of-Houston", "place_id": "ChIJq-m4EX3AQIYRJkn4Lhccp2E", "address": "1800 Augusta Dr #240, Houston, TX 77057, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.42318089999999, 29.7345943], "type": "Point"}, "properties": {"photos": [{"width": 750, "height": 437, "html_attributions": ["<a href=\"https://maps.google.com/maps/contrib/106788706324997826205/photos\">Erika</a>"], "photo_reference": "CoQBdwAAAPpSBcAwBW3x2JngST7pQDBPefFY9ZWhbHSoPLEmxeXdKrigO6ld9pgBGlkHi8ANcwOiq18SAJzsOYUeol1Ex7zxXLOw2-EzTNBck6TJGm0-HbXRbaXTfzV__EenaGACh1D_6xTmuKAwlTzkSzTaqR_zl94R8afHsjmKyYliIpHjEhDgvdOZo-f9V7CNkkHpKKJiGhQBOJoiEUb2Ou7nNiC19-YmbMW1VA"}], "types": ["point_of_interest", "establishment"], "reference": "CmRRAAAAi4VgKKBpHyg1KI6g-M8mRD-IPB2RLp-QOGltQjZ4XuGyPcEHfrxZnRh7rvg46wRjOcCXaa8-i81zfc3NbYVhFcsKq_HaChOahM1pxLyzG_5kUeA9C7_OB6iYVdTTh5nMEhBfpnyrmF_4urPTB-OuBpSQGhT2fe-3pwNGLLYXAz3HExzWYmWsPA", "name": "Student Conservation Association", "rating": "NA", "id": "1c5ea7722fc0d99e9f7dfca55f5d9078224d51d3", "job_title": "University-of-Houston", "place_id": "ChIJQcqBXfDAQIYRErawO-goGj4", "address": "2990 Richmond Ave Suite #400, Houston, TX 77098, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-96.038102, 30.055621], "type": "Point"}, "properties": {"photos": [{"width": 984, "height": 985, "html_attributions": ["<a href=\"https://maps.google.com/maps/contrib/110279808588468038448/photos\">Peckerwood Garden Conservation Foundation</a>"], "photo_reference": "CoQBdwAAANSwReulyvtUSXIA_cTAUOq-qglbywR5h6WaaaUJg_yGxDX36mf3OVh3Pz0bO7unYM9I_2riSr2U6Emf3wRk3KQFBXyrcjMg6B5bPGEZSKE7FHUCYAWjgiDs-QmsZrXbwTlwrhw6ExxACt8FiDyY8q_jxnhSpT6Hc8eaqq3a-q56EhBxIlWs_sXwPLm24qVpN2_pGhRkQpLq7qli_Zvm-HV5O7Wburg-bw"}], "types": ["park", "point_of_interest", "establishment"], "reference": "CmRRAAAAnDrFxiplRzsyiePUL86N7fn5GAA0YwvT2IoyecHknSnqPWDXk8-Q89TMIZR9ig4PZ_EGE0zIbx-LsY0gqjTo-Oty5pRBXqfJOxsKjt3jhpbN1pX8IyFZJkk82jQRqZa8EhBEtDCi0xnR0bT77jl1Y50QGhTtz4VQIvQmhtInJO5IZCjInukUmA", "name": "Peckerwood Garden Conservation Foundation", "rating": "NA", "id": "e618a4c618cd67ce4f5fdc165f640220ab3b53b2", "job_title": "University-of-Houston", "place_id": "ChIJmUR7pvHKRoYRIIl0o73bPGE", "address": "20559 Fm 359 Rd, Pine Island, TX 77445, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.64386449999999, 29.7515036], "type": "Point"}, "properties": {"photos": [], "types": ["point_of_interest", "establishment"], "reference": "CmRRAAAAgHu26lbGGyu5VK4ms66PBTLRjQes78daaNJdCN1XR00MOyMlp4ausmWtgw0VaoHpjVcujsCQjJu4oQ6VYk18n67edpeaLeOOOEpn5Guh9oyZtMAIq40HTLGi8G2apUt8EhBpGdcx1gL7g73LPyhMNNU0GhQfV6dU5C7p4KvSiO6K5oswgTAYDQ", "name": "H2O Conservation Technology", "rating": "NA", "id": "30c07988ef8dfc62dac712b9d587daa4a36f2539", "job_title": "University-of-Houston", "place_id": "ChIJIWZRKeHKQIYRXxta3wOMGGc", "address": "1725 Hwy 6, Houston, TX 77077, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.5705632, 29.7714443], "type": "Point"}, "properties": {"photos": [{"width": 3024, "height": 4032, "html_attributions": ["<a href=\"https://maps.google.com/maps/contrib/108143329814504597326/photos\">State from Jake farm</a>"], "photo_reference": "CoQBdwAAAInUcczZNqeFCMg-c5v--gN0JGDTZTI3P4zp4aIeS_uv3ig-K6vcfIJ0zERaSSXg2K1dltheDZVQgdNmfzP-jEXuCpciZsniYFuRGCRoZNjBRiKW4zawwwzkQmvk0h8ZhVMv965Tuy5GeqErNK0_hZtMO--Gk3J8tGHyv8eUYzCtEhB0una2oTOS8E26PfkQNjGBGhSMqSr5039H7xiQ159llKh0bO3hEA"}], "types": ["park", "point_of_interest", "establishment"], "reference": "CmRSAAAARsIGFe9B2RJZJjeo1u4-lJNZDllRKPRtXeHyAjCSvospw7Ez-czjKHHzohV_eBzTAhDI8dVE2DYVeldRGjrSjKTmj40k4g00jrQKaJc9DiA03ClF6LaXRXhA3SpMPNeNEhBF9YU_e38f-HtuZGA8ebsRGhT29-2J_P4tGywJb13vbETyumXiYw", "name": "Houston Audubon Society", "rating": 5, "id": "050a5458d86bdd1cee7b09678bd6256d0a20a73e", "job_title": "University-of-Houston", "place_id": "ChIJlQOxwVDbQIYR2uX_TZl0TYc", "address": "440 Wilchester Blvd, Houston, TX 77079, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.56820189999999, 29.770778], "type": "Point"}, "properties": {"photos": [{"width": 1800, "height": 1200, "html_attributions": ["<a href=\"https://maps.google.com/maps/contrib/108765250995932379967/photos\">Audubon Docent Guild</a>"], "photo_reference": "CoQBdwAAAEPVL9IxAAUeJNb88jh9SB0UIeZv1zDmy3qqWRfCJEMuvYlYxr0F_q_SA2dtSSXsL4a4S8X9_lb9r0IAVV087DbllosuU8u9FI2xH5xTp9UJute9g5fhR7kGhbOd6G6rdM8IzLiv2YBWoQr7j7jDkMRVv95UXBGzpbtHFW52UPSrEhD8f-OUpUVg5AKzkuF3gCwfGhQWwsv2Y5_WRaPE5olbO-EwWeazeQ"}], "types": ["park", "point_of_interest", "establishment"], "reference": "CmRSAAAAymaUNQ5nZHivVk86bq2BwYdX2qP7yavlxt1mv8ZKQgbeI5fahtwVRKEmJgq5sFAeBRMGD_bUu9WbbG9jXU0LOi-6T1YEvkvTUqpTfSMeKhPIoq-hk2_PeFd6eU_UpXZsEhA0jOn_q4rn6sG7FMkn1Q3cGhQTMOUFepBPWe6SwFBEXfKWtlyx0A", "name": "Audubon Docent Guild", "rating": 5, "id": "7ddd5daf76cc4979e2ba6b062322d1c77d5d1c07", "job_title": "University-of-Houston", "place_id": "ChIJI9XyNFHbQIYRtwHb8EtTpeU", "address": "440 Wilchester Blvd, Houston, TX 77079, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.44932349999999, 29.7803218], "type": "Point"}, "properties": {"photos": [], "types": ["point_of_interest", "establishment"], "reference": "CmRSAAAAmu4UFVQcDNcDQ43HR7WI_uBpUI9NsuHn6rssEJ_HJ_p3RZu8WJD6wCWhj_HjQvbt-lkXP_wZVQ_Fs4BgLbjvPLGGFxCoL3Kkyw-YnRGkuVcXtERDq6qKSnlgV6I5wjNIEhD68zCyNEywN7jC2LnECYZLGhQWwAEBp_WsWeWiM10pzybmMklJ6A", "name": "Coastal Conservation Association-Tx", "rating": 3, "id": "7258b034e119f31e82320bca6e72781ee9f79d75", "job_title": "Woodridge-Nursing-and-Rehabilitation-%28houston%29", "place_id": "ChIJcekacM_GQIYRPzL13cgQrPk", "address": "6919 Portwest Dr #100, Houston, TX 77024, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.47039, 29.655454], "type": "Point"}, "properties": {"photos": [{"width": 5312, "height": 2988, "html_attributions": ["<a href=\"https://maps.google.com/maps/contrib/101184977609161362375/photos\">aug4</a>"], "photo_reference": "CoQBdwAAAD-oeLB0L4SGnJDFP-YM694HLBUFjxF4OXzbWcLsgFe-W4TNBF7b9NXmV9BJ1JPhxtn08ld6_74QYjK9_wOAzE1RLYCgqm1gbndMJMqVy0mSvCkYoSyzGru4-ScS0OxNWsolu0wC4KJR1j0NsmcvN8pUvR3V6wmdapQwTi7mpalAEhBDuucmKUOk0WQcCQz0FnkuGhTDz6_lLailGpVGW3Zn5Oa0J6LC5Q"}], "types": ["park", "point_of_interest", "establishment"], "reference": "CmRRAAAAqYYilRbgMUb17y1wlU86PKkP1rGIYJ4EYCL0UwquQEExvqUxtyihQBYwkVJIzmDlGZC5c61UY8yVIBQjWV6S8qsapY6WBKKzEqFkBEFjKfpFCYH5ztHueulp2mNDpa6wEhBqPD5MTcOWXsDG5dY4-aUqGhT6sUf_mLByQDrBYtBWXdPJKWo6Gw", "name": "Willow Waterhole Greenspace", "rating": 4.3, "id": "0127506e8071350c2d48f0ca56e939045297a0f4", "job_title": "Woodridge-Nursing-and-Rehabilitation-%28houston%29", "place_id": "ChIJR6_2zTzqQIYRsA7wExgfDWs", "address": "S Willow Dr, Houston, TX 77035, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.4003322, 29.7388505], "type": "Point"}, "properties": {"photos": [{"width": 1136, "height": 640, "html_attributions": ["<a href=\"https://maps.google.com/maps/contrib/117056878997299689379/photos\">Marisol Brown</a>"], "photo_reference": "CoQBdwAAAImOiSx8HFHfbBXZlwJ3XSeB4VlWqQ_LVBhxcuRwI6hhhwVJKdYq2TLdrwPh9Pet6dZpegQeB5gCEv7ix1Juux3cNwy2B34cPGzaa5rDeJ7JL_yZpuMhM_ZCKvDAZcXiig7RqAloDZxf6TAqLEIKH1WU1iKGqsrwq-r7DpcZhA9lEhD2Nquw0VIUycBfc3_O9nW3GhSmWNAU0K3SJDkAID-GwcVrH9tCbw"}], "types": ["point_of_interest", "establishment"], "reference": "CmRRAAAAlJNGTq5o6o2RjMG3gmIby4cnBVRjcpNxhsotJXAl0QVSG5lxMRZ2Pk9kBH34SwjwPdh1ogjxNKlh4xtkoep6tlxlhJKH-yyC-K94Yb0tjelj6Jj7m6_kN15JnhdZs6yCEhDMT8pprtN-vAEWmoFkUmWVGhScgDdh-izlRGDhleXC32PGbMWS3w", "name": "Masters Fine Art Conservation", "rating": 5, "id": "a462c2eef4e22ea319485ae7b84f3d20756cbdd1", "job_title": "Woodridge-Nursing-and-Rehabilitation-%28houston%29", "place_id": "ChIJp8u2bZvAQIYRbosnWz6cVmY", "address": "1612 W Alabama St, Houston, TX 77006, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.3876169, 29.794149], "type": "Point"}, "properties": {"photos": [], "types": ["art_gallery", "point_of_interest", "establishment"], "reference": "CmRRAAAA8yu6syIvfmEgrItX5fOWg148-BF05G1ZNJ2sRlvl04g9LTk0z0Mctaa0QU1QtUR5J1BxMWprM7ksFoyVtgkYT6jZAM7od5yMNArdW5EE5UR1KFyOoobA2mNQ6dXcU5WhEhBRZ0ZhWZzrYqe7f3v4VOB5GhQ_1jhB5l6RKUFxA_d_CGoLmRclUg", "name": "Whitten & Proctor Fine Art Conservation", "rating": "NA", "id": "883a8c5ef35ab28e1630235ad65a6b16506a67fa", "job_title": "Woodridge-Nursing-and-Rehabilitation-%28houston%29", "place_id": "ChIJ8YuXE6K4QIYRn1SF1hazFEw", "address": "1236 Studewood St, Houston, TX 77008, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.3858767, 29.7300997], "type": "Point"}, "properties": {"photos": [], "types": ["point_of_interest", "establishment"], "reference": "CmRSAAAA32Dqnv4gk1CCPiO3_eUflNz5zfE1i7mR8BiRNhcoCKTHWLODExSOUuW9eTRFneakkglv78YlCBXCp3lDXxdLeu7T4wTAaPoZNi0QjMFqki2CwT1D49qDGCoOagAJIPklEhAYU0l0IPbrWZVMMuNiLG7iGhTgP_54F2I0pKpUT3ELkytK7pi1ew", "name": "St Mark Fine Arts Conservation", "rating": 5, "id": "ea2d4bac6d74716b33f456dff3aae0cc0b43cca3", "job_title": "Woodridge-Nursing-and-Rehabilitation-%28houston%29", "place_id": "ChIJKbDEoXm_QIYRcRFBlp0dE8A", "address": "4901 Main St, Houston, TX 77002, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.483218, 29.7482286], "type": "Point"}, "properties": {"photos": [], "types": ["point_of_interest", "establishment"], "reference": "CmRRAAAAFTLOB97gtaeRdV5YY6GaEsMQiffs44PhsaKoUOL3jU0SVVf2Ftky44ybvZ8vsk8JxBBNvM2iEKHPQs8ZGk0FYQnjDwsSFIdthdsVyhWXVYmWYIFe-1yt-6RjpIn37wa_EhBpkSunExwhEKOdyEMo8R98GhS65KR6ZkM7YJ0J6sPbChcB9Kaf7w", "name": "The Nature Conservancy", "rating": "NA", "id": "90af6fb9fb926dde9f7103577cebc4150bbb1dec", "job_title": "Woodridge-Nursing-and-Rehabilitation-%28houston%29", "place_id": "ChIJq-m4EX3AQIYRJkn4Lhccp2E", "address": "1800 Augusta Dr #240, Houston, TX 77057, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.42318089999999, 29.7345943], "type": "Point"}, "properties": {"photos": [{"width": 750, "height": 437, "html_attributions": ["<a href=\"https://maps.google.com/maps/contrib/106788706324997826205/photos\">Erika</a>"], "photo_reference": "CoQBdwAAAERrok2uCebu_8s3lw5Sn98KVYotul_COYdRxpzJUKrhQg7RleFpJ3zueFKi3ipIzC_NnLAD0A1TcorOFo4XajAd1apGrslzL90vWx72QBaGEOfZhr1CX64WX80aIROwy63COF11jsauJWUpEE1J95g7461OVhJD_iRA8mCtEpaNEhBsqkwmjVWgld_xPANGA1WMGhTKHe4Qlg47Ii0_jXo2uJMRBwPjow"}], "types": ["point_of_interest", "establishment"], "reference": "CmRRAAAAiNp7sSOmzhH0iQs9gQ5zuQnOOyG8z3ND5QtD_eISOjFdVv-ZD4iV3HdjhQ5wfLy9SodPNLhQpcCSqzypW5g5NXjEag1YHblsUo0OW2QzLpZ5KWE8-rYkl34XdyjTpr-rEhCR9hsYsKdimj3HrsYCfovMGhQWLkWgHoTfiedTFgnLs49AOBjFow", "name": "Student Conservation Association", "rating": "NA", "id": "1c5ea7722fc0d99e9f7dfca55f5d9078224d51d3", "job_title": "Woodridge-Nursing-and-Rehabilitation-%28houston%29", "place_id": "ChIJQcqBXfDAQIYRErawO-goGj4", "address": "2990 Richmond Ave Suite #400, Houston, TX 77098, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-96.038102, 30.055621], "type": "Point"}, "properties": {"photos": [{"width": 984, "height": 985, "html_attributions": ["<a href=\"https://maps.google.com/maps/contrib/110279808588468038448/photos\">Peckerwood Garden Conservation Foundation</a>"], "photo_reference": "CoQBdwAAALwXvRf8gB0o4C_JHsOVWVcAScPXMFU62ngD2bXDmcVYS3EaLeNeqbTwYA-i2-tqhrSw1gsqojCLAKjc2YlCzmbLLKjOUGgi1L1BftZ-uCpihVc-M-YSHrpq6FexcO-CN11Y8tSrbhxUxf_mpZkIEeXwUHfQHMe2AK79KYLrELpHEhDmNv2tRnlZJ2N_jlLJSR8MGhRXrEYDCXZwwqoO06vehvBcsFPZlQ"}], "types": ["park", "point_of_interest", "establishment"], "reference": "CmRRAAAA1dGBbBvzImuXgD5KPl9PmuTbiFPvg4eIbiQDA5E66SOF1mpGUC7C_32obNl7EuS94gikwkYrZDGo9Ck75fQ2EZS1QjUqwxTtSfylPA0RcFKyXUBXYQs3k61aGoSdLNzTEhBFdy-YHt3Il3f4ga7oh_N3GhSCJ52Pd4_mHPhfjgGtFylh1TKN2Q", "name": "Peckerwood Garden Conservation Foundation", "rating": "NA", "id": "e618a4c618cd67ce4f5fdc165f640220ab3b53b2", "job_title": "Woodridge-Nursing-and-Rehabilitation-%28houston%29", "place_id": "ChIJmUR7pvHKRoYRIIl0o73bPGE", "address": "20559 Fm 359 Rd, Pine Island, TX 77445, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.64386449999999, 29.7515036], "type": "Point"}, "properties": {"photos": [], "types": ["point_of_interest", "establishment"], "reference": "CmRRAAAAV_NKNNQT9rlVvZ0o5dRTfRC5i9XVaUT0sk6k7mgxBsnLt5Exf-9eO-NxdW5G2e8OKt0Bs5yCQWVzaOfuMe_MTH-MQHchTYaD4Vd8z9sKA_MVEiFPXPVpneILqOGzME-IEhCD5xjDN7m9PJ0yqmT2mR8iGhTTKRe7167TKp-sR1teku51FZeQNQ", "name": "H2O Conservation Technology", "rating": "NA", "id": "30c07988ef8dfc62dac712b9d587daa4a36f2539", "job_title": "Woodridge-Nursing-and-Rehabilitation-%28houston%29", "place_id": "ChIJIWZRKeHKQIYRXxta3wOMGGc", "address": "1725 Hwy 6, Houston, TX 77077, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.5705632, 29.7714443], "type": "Point"}, "properties": {"photos": [{"width": 3024, "height": 4032, "html_attributions": ["<a href=\"https://maps.google.com/maps/contrib/108143329814504597326/photos\">State from Jake farm</a>"], "photo_reference": "CoQBdwAAADDW5hzHkVQgepvAmdck60ha_DXYj7vMzmt6rSIEvvYHIESbAj4MeFlX0bkKXUw0W3uD1x_bNKg58ZRyHjpdp8wGhpehuH6zaL3X6D69rOJW8Z_1I2xy9TAyrTBsNcZLD48br022FF90MFbhAAYLpHuD5dbzx9lEqcxW94s-IAaoEhD2Ns0FGi63uzOp26HO1HN1GhR_eNNDbZ-7nehctljUBb0QwximoA"}], "types": ["park", "point_of_interest", "establishment"], "reference": "CmRSAAAAM6yOjnSh2byrfnLnLcXhO7udqojCiYYhR1GW_p3jERMr0VKUoCzyzT9ct19fjBAvJfvgse7UgiXD4RqVzMW19OkfwEXUpLxhI9VTVRsKJEYfKSSyYx6VqRL8IYTNFM-3EhCA_avCp83dRFLZzasHhAAFGhSv2rs-dVQz3f5CpO_VqSdWjzQwFg", "name": "Houston Audubon Society", "rating": 5, "id": "050a5458d86bdd1cee7b09678bd6256d0a20a73e", "job_title": "Woodridge-Nursing-and-Rehabilitation-%28houston%29", "place_id": "ChIJlQOxwVDbQIYR2uX_TZl0TYc", "address": "440 Wilchester Blvd, Houston, TX 77079, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.56820189999999, 29.770778], "type": "Point"}, "properties": {"photos": [{"width": 1800, "height": 1200, "html_attributions": ["<a href=\"https://maps.google.com/maps/contrib/108765250995932379967/photos\">Audubon Docent Guild</a>"], "photo_reference": "CoQBdwAAAGI95JgfltEv2625Q2Ldkri0cPFj9ki9jEfQT8XECDe32G85B5X0CsJiSlsIcLnrYvuOxn_NG5szGc9869MKBx-QTHj3lP4oHGvXNhCtqfDaCyRHcj1fSs4Nj1VK2PI9Qg_2FUzN9JSIbjpX_VRiZj1lApxG65zGp2SWBPTkw2yHEhCzC-NcZ26uedjF6KWR_mfYGhSLCg09ZhPzWHH1muW9KHD1qQoW9w"}], "types": ["park", "point_of_interest", "establishment"], "reference": "CmRSAAAATP3MWzoLr1wGbi-BP6gUIjU-uHDNgYDjyBl7gA57fpztRtlPo4hOxlsGHog_1zF7jGcojZzD7TGw7HVSO2roJlBm-rNaLbZS7SgcxZpd7RJA1936FzQZHrOC-wvaKc8SEhAy4PDQFSVFKAkLP5PET00IGhR0wAfmvNgwX3yw00mZNqNgOndQXA", "name": "Audubon Docent Guild", "rating": 5, "id": "7ddd5daf76cc4979e2ba6b062322d1c77d5d1c07", "job_title": "Woodridge-Nursing-and-Rehabilitation-%28houston%29", "place_id": "ChIJI9XyNFHbQIYRtwHb8EtTpeU", "address": "440 Wilchester Blvd, Houston, TX 77079, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.44932349999999, 29.7803218], "type": "Point"}, "properties": {"photos": [], "types": ["point_of_interest", "establishment"], "reference": "CmRSAAAAyDH9-WhSuQUgbv6WB5Hmsci8kZKLk_is0SK0p6Omae9dw-D9fSh-4rFPG_8tJhK_J88gOnefFrosoth_GuRgpHlWygBZwxFMVZN170IKOXPRQMa0euf_pxyTyUwXDFCmEhAe4kDdccspPjjny7Xxk2WLGhTBbAIQAO1gyYFUNpisi1kXZCJz9w", "name": "Coastal Conservation Association-Tx", "rating": 3, "id": "7258b034e119f31e82320bca6e72781ee9f79d75", "job_title": "Starr-Companies", "place_id": "ChIJcekacM_GQIYRPzL13cgQrPk", "address": "6919 Portwest Dr #100, Houston, TX 77024, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.47039, 29.655454], "type": "Point"}, "properties": {"photos": [{"width": 5312, "height": 2988, "html_attributions": ["<a href=\"https://maps.google.com/maps/contrib/101184977609161362375/photos\">aug4</a>"], "photo_reference": "CoQBdwAAAGd8ERBHgqOMK_fop8kEEQA3o8aozMu6JRwp4kM8NzQyT1NIQYE2ZN7s9fjCbO2LDx5PjW1CtcjRZe8XYPM99Tla7TePNn_aM3PcFp9G56RSFJYZai9x8x3lweF9qZwUxNNAvuEXCWqslJxNmoalUvPyeLCXoDyXJjxhH5nb1rWeEhDa3E3hIpSJ1tYTgBzNSmHtGhQHp3Cxg8ZqPWxp3WeJV94dwgeOSA"}], "types": ["park", "point_of_interest", "establishment"], "reference": "CmRRAAAA4sZ6wtfNzZYP3cibzL13xQtmMYS0JnkslIT-DqW7tqfIP3xIkADDdiSPTk28vjyN2s73AdzAgcJZknVt9cGhX3qTrLmQC9pepzGamBWCZYgUxZxsIr-r1QdBcxlW1Uk0EhCwSN7B-CELzD3wikqRgY9fGhSvHef-BJuhoBfVssitReCo79C1Bg", "name": "Willow Waterhole Greenspace", "rating": 4.3, "id": "0127506e8071350c2d48f0ca56e939045297a0f4", "job_title": "Starr-Companies", "place_id": "ChIJR6_2zTzqQIYRsA7wExgfDWs", "address": "S Willow Dr, Houston, TX 77035, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.4003322, 29.7388505], "type": "Point"}, "properties": {"photos": [{"width": 1136, "height": 640, "html_attributions": ["<a href=\"https://maps.google.com/maps/contrib/117056878997299689379/photos\">Marisol Brown</a>"], "photo_reference": "CoQBdwAAANKVn3ARV0kyWekMMxJZNgKmzXdz5MYlmbGDZELAAtHZGl8qElXX_e_AP0t2SHy9-LShtALDVH995ovF-Bina9ByPffbUiLdHEpheXp92olDR3OwLeHARKrerVms_snWNDb_BHwkrTfi2T7lt404tQKhW0HqaHV8rnOtOAgy6m8SEhA2sOIqLwuR7PKnZhcfkkvCGhQIX2lDFZalK1tc_hdiH7dxuc3l4w"}], "types": ["point_of_interest", "establishment"], "reference": "CmRRAAAACUQPSxWrE4Izh_Q2085scF1E3om0eew1EazwNCsHa3T_UFD7Q7pxb0e8-Pg5yEfn5Wi8u2uQoaKR1FCTa9AGBYovm-VlQYhmfvvK9W-cWBD5iq8rjLtHVbzX9s3mmSmpEhD-n74enLvSomlAva70fDm_GhTqxjRwLGY8wVpwHAubyjPeW_FDJQ", "name": "Masters Fine Art Conservation", "rating": 5, "id": "a462c2eef4e22ea319485ae7b84f3d20756cbdd1", "job_title": "Starr-Companies", "place_id": "ChIJp8u2bZvAQIYRbosnWz6cVmY", "address": "1612 W Alabama St, Houston, TX 77006, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.3876169, 29.794149], "type": "Point"}, "properties": {"photos": [], "types": ["art_gallery", "point_of_interest", "establishment"], "reference": "CmRRAAAAp2E7NpkCMa4T993WIv7RYTVQQpxhB9mvPFBNWZ4tR4EtcpUTJIeXIicMdLs1fTSZMn9TP3OUDXZk0vwYCkJwGD3zgxT6atOsQZJqIKgo0GKqlFDmChOvcuoGhn_2sTcVEhDyamKlBOhMr-YdspdBu-h9GhS3IY1goVa_weOE8q5ptAk3SQbZNA", "name": "Whitten & Proctor Fine Art Conservation", "rating": "NA", "id": "883a8c5ef35ab28e1630235ad65a6b16506a67fa", "job_title": "Starr-Companies", "place_id": "ChIJ8YuXE6K4QIYRn1SF1hazFEw", "address": "1236 Studewood St, Houston, TX 77008, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.3858767, 29.7300997], "type": "Point"}, "properties": {"photos": [], "types": ["point_of_interest", "establishment"], "reference": "CmRSAAAAenoO0NI1eilmMcBum6dI79V5oA5lBJknMkyh03tVC4-wrcxQnqOZDCmFH_V7pMEp2rOAfSryxdL9c53nQpnA3ODhtRP0hN4pa8ZNPHWOxuuwlaFqXTuIBNTd6yFU8qnrEhCbWHbQ5jRA_ON8P-rxdyB5GhR1g0SLqiHps9Yc-8epB9akrqdb2w", "name": "St Mark Fine Arts Conservation", "rating": 5, "id": "ea2d4bac6d74716b33f456dff3aae0cc0b43cca3", "job_title": "Starr-Companies", "place_id": "ChIJKbDEoXm_QIYRcRFBlp0dE8A", "address": "4901 Main St, Houston, TX 77002, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.483218, 29.7482286], "type": "Point"}, "properties": {"photos": [], "types": ["point_of_interest", "establishment"], "reference": "CmRRAAAAsD5dX_TnYEPiDzPh9aJ3hopnPRZ0bSBe4sBHr3xghK0n6UyPppTP10DvmwJytkpAF9wNippvGTevAaCHQvZKPPQaWbAXatqiqF27uf3yjrD5eYyK2pEG-K8HzdkeaoJnEhC0K3DS-AQP2WY_24iJ3l4iGhRkkTeq4w72-B_-oKFjr4z2igCevw", "name": "The Nature Conservancy", "rating": "NA", "id": "90af6fb9fb926dde9f7103577cebc4150bbb1dec", "job_title": "Starr-Companies", "place_id": "ChIJq-m4EX3AQIYRJkn4Lhccp2E", "address": "1800 Augusta Dr #240, Houston, TX 77057, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.42318089999999, 29.7345943], "type": "Point"}, "properties": {"photos": [{"width": 750, "height": 437, "html_attributions": ["<a href=\"https://maps.google.com/maps/contrib/106788706324997826205/photos\">Erika</a>"], "photo_reference": "CoQBdwAAANXgqMWtmXIjt1yeGOF3dF3C2YEQ0Qz90fuXxez5Dzw88iWBnLjc6bQyzKW1mTfEhPRBEpJwbD0YM70y7l_-zEReq-O9jAFkqeA64jeuGbYi_kaHyMHp7VmO_KQFkwANIBkbIIMvvXS7txNbIKq2lxGzlV2OCnd72lt9j_4M-kq5EhC6UrFauy2VQ1EAWNzkFd0mGhRLQh0V1rw6sm_VdDGHnjgVL02jRQ"}], "types": ["point_of_interest", "establishment"], "reference": "CmRRAAAAp-SpCTMb7bnju-SvPGPy1gfPy_6r5Dln_ssZIidsWUHJhjSbF7m4QnElv6wQFyvu_hRFECpGYvfwmNhlbpw-ejrWMTc5kclprdAqb7ZhMH-2x4XQ6GAP23-x4S8k7p8eEhAzeoitfFpZh-lG60_j5scWGhTI8-CSUhQG1Z70aVxwLLryhf8SgQ", "name": "Student Conservation Association", "rating": "NA", "id": "1c5ea7722fc0d99e9f7dfca55f5d9078224d51d3", "job_title": "Starr-Companies", "place_id": "ChIJQcqBXfDAQIYRErawO-goGj4", "address": "2990 Richmond Ave Suite #400, Houston, TX 77098, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-96.038102, 30.055621], "type": "Point"}, "properties": {"photos": [{"width": 984, "height": 985, "html_attributions": ["<a href=\"https://maps.google.com/maps/contrib/110279808588468038448/photos\">Peckerwood Garden Conservation Foundation</a>"], "photo_reference": "CoQBdwAAAAbay6FOeT7rik1dLi6Ak8igZYvll9afFD-HYy1RKOFpxU_1zDZuHpA1SQ35PEZoINCYyJquNUxNn5xe2jOThiJdULptO31uSYZn9dENnx_9OCaDORr987FOkGGHkllj0m7LDv357ed6HS1Iv3czRYTerqngW8rCBXcW1o8EcgGREhBiXYfOCw0b4p26e1SddeF8GhSp56ZKK9wHPROlgAFM2mTQZD-6Rw"}], "types": ["park", "point_of_interest", "establishment"], "reference": "CmRRAAAAS1EEPZ22jy-kSECLv1VnRa3oNywYiAVxd9EQ1wZUTeTKS9qFp6G3bhoJcytiNX3qJOGG-5-tjE2oF-UqXpEUwudwF8JPUXYenufuIthPkpVU0u3JNcFqS6_WvO01mkOFEhAHT7BEJ5j5VGrlQfZcPakBGhQwP-bLFsyKjzd1gmkSeYJI6WclXA", "name": "Peckerwood Garden Conservation Foundation", "rating": "NA", "id": "e618a4c618cd67ce4f5fdc165f640220ab3b53b2", "job_title": "Starr-Companies", "place_id": "ChIJmUR7pvHKRoYRIIl0o73bPGE", "address": "20559 Fm 359 Rd, Pine Island, TX 77445, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.64386449999999, 29.7515036], "type": "Point"}, "properties": {"photos": [], "types": ["point_of_interest", "establishment"], "reference": "CmRRAAAAoZNpejw94TrrRU51rXi1iTVN6i13ysHfizJHnJQliabWaeu8Hd1iuzdLTAqfv52t9ObEybkbSthaUXmiUPW8JUL6hcfKpeIAA_6I54MvglyZg7xm4WOwCT9ccYEwZ1rPEhAAjTL71WapQ7wX0xQtFXS7GhRyH69982QCzwRMsfAFpN-9JaaHXw", "name": "H2O Conservation Technology", "rating": "NA", "id": "30c07988ef8dfc62dac712b9d587daa4a36f2539", "job_title": "Starr-Companies", "place_id": "ChIJIWZRKeHKQIYRXxta3wOMGGc", "address": "1725 Hwy 6, Houston, TX 77077, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.5705632, 29.7714443], "type": "Point"}, "properties": {"photos": [{"width": 3024, "height": 4032, "html_attributions": ["<a href=\"https://maps.google.com/maps/contrib/108143329814504597326/photos\">State from Jake farm</a>"], "photo_reference": "CoQBdwAAANv5Tl3cVH60IQEeRFxp8WhBj36UB1mhmGCA-dXF9TFChabbjY4iGmH_JWR0DIPbxfXJeA52agegeW0AoT-RSqulLHY3p4hi1cxlpfpp4aBqbvm8_9fE0de_Z2diMKQ3zRUcpNX_dYLLbBaKkjoPBJq6Vpw0TyroTKRhNaKY8qKKEhD28T1GWBE7PNMP9SDmXyCYGhTOseH07aBpoq3xVUSW6zg8gMw4yg"}], "types": ["park", "point_of_interest", "establishment"], "reference": "CmRSAAAARvMnszYuoW88UEW2eVRfBQk4d167ahOh0qmAsl01vdtKZtDYyqEqmWDm2gGShYXzlB3GDxzcKKq9d_G2WOjekPSZT9YSchUL7T8Z3CeX195d5_3iokI8whQ_CWPPVR9yEhBgO_0isQAB0akK85911cIgGhSKOF7Ms8EFlbZMAJzxuE7mTZ5uXQ", "name": "Houston Audubon Society", "rating": 5, "id": "050a5458d86bdd1cee7b09678bd6256d0a20a73e", "job_title": "Starr-Companies", "place_id": "ChIJlQOxwVDbQIYR2uX_TZl0TYc", "address": "440 Wilchester Blvd, Houston, TX 77079, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.56820189999999, 29.770778], "type": "Point"}, "properties": {"photos": [{"width": 1800, "height": 1200, "html_attributions": ["<a href=\"https://maps.google.com/maps/contrib/108765250995932379967/photos\">Audubon Docent Guild</a>"], "photo_reference": "CoQBdwAAAEnoQ2S4f_fkZ49YelwNHPWb2T43YFdB-NQ3jcoPF8j9P7WhrUYpcUKjlOeEtZSVvGEuGZbzxnTtAgrpzing84jn8ofVSasVBb9OJUOVXhDhSeOYK0ZuujAdP6xoP8zRooewPnwc1ipS-lm_PQ3HydRIeF9sDgOM2Eo1-dJCHU6rEhAUyqBhTzemCaeA6zsuOwD4GhTvklLDPTIT6Y82_oNhQPiwDeGH7Q"}], "types": ["park", "point_of_interest", "establishment"], "reference": "CmRSAAAA8nSljgf-8gy_UTaOikndHl7wmUZp9qcCgR3FWJGApUsaKPupljE6AHc1I9TxOqoM1V0DyceY81a5kB3d9MQrAZJBcgvd9E6J1xKwBLD5wV1nrr0C33Pp2QtOt2tmV9D1EhDgapZ21AlPv4la51ASyTaFGhS9Fp7C_86dGwfYD7aW3-FOA7_mMA", "name": "Audubon Docent Guild", "rating": 5, "id": "7ddd5daf76cc4979e2ba6b062322d1c77d5d1c07", "job_title": "Starr-Companies", "place_id": "ChIJI9XyNFHbQIYRtwHb8EtTpeU", "address": "440 Wilchester Blvd, Houston, TX 77079, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.44932349999999, 29.7803218], "type": "Point"}, "properties": {"photos": [], "types": ["point_of_interest", "establishment"], "reference": "CmRSAAAA8TPPIbRQKKcHqEoTKHVbn_gAYuakTRMwMc_n9v1MeXw6OuV3TU11kneGaD8LFau3jR5I1PhxBSXTSC4XO3LE40VmR45y8r25M58Zx4Y1i-_pIXdzXhAgGiqLzE-g5prbEhBzHuqLf6TxFGZnjrVQ3DJ5GhR4y1ZePjedgY9sZH7zX9I7FS7rbA", "name": "Coastal Conservation Association-Tx", "rating": 3, "id": "7258b034e119f31e82320bca6e72781ee9f79d75", "job_title": "Servomex", "place_id": "ChIJcekacM_GQIYRPzL13cgQrPk", "address": "6919 Portwest Dr #100, Houston, TX 77024, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.47039, 29.655454], "type": "Point"}, "properties": {"photos": [{"width": 5312, "height": 2988, "html_attributions": ["<a href=\"https://maps.google.com/maps/contrib/101184977609161362375/photos\">aug4</a>"], "photo_reference": "CoQBdwAAABfrN3K9IPv8nn_gsv3fw_e-n4iZnEP_gnw0eBgw-94k_cq7J2kiVRpsbTheAE604YURoCvQHkKcN5yKIBToCK1lWRGR5SaFyGt5sk_dzoq4WCO7QEhSMELIBUfK2XFQBHY-4AmrvEdAGrrvvku8OIXaRzKOHFR4on6rirP9r7-0EhAQucmFFKDsSLxk8pzhyvknGhQhT4PhLOrIQ4txiK4-kaCfBVFNRw"}], "types": ["park", "point_of_interest", "establishment"], "reference": "CmRRAAAAg00ViJY84tdilfVtBiHmmhVjTvZ-IEriufFZamBIwD-xRjQ9bet8A2TvyFpwFyt9Xq3NCZ8628dSyzUONgYkeLXhamjoMGeCtt0zyjX_2-mlygWCeu-U__8z2nKaoIxJEhA_lu72xABEUk8VZhPXWMQeGhT3JmymrWIELZS9pr_OmtMOxWy75A", "name": "Willow Waterhole Greenspace", "rating": 4.3, "id": "0127506e8071350c2d48f0ca56e939045297a0f4", "job_title": "Servomex", "place_id": "ChIJR6_2zTzqQIYRsA7wExgfDWs", "address": "S Willow Dr, Houston, TX 77035, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.4003322, 29.7388505], "type": "Point"}, "properties": {"photos": [{"width": 1136, "height": 640, "html_attributions": ["<a href=\"https://maps.google.com/maps/contrib/117056878997299689379/photos\">Marisol Brown</a>"], "photo_reference": "CoQBdwAAAGGbuTs5GcbNAuj9XKEXKBNKmqg_Kvaruh8AYWUyUm_4Gr-2UZmUROWNZco_X0_iXd6FP8RdbJpDaJcCFAP58HOUduopkA1FTvDqEJrASTCQJeMdSxaZbX1IZi81pRHxQnlP7NlQT1_ItDrNYnOaiPHiHwzeu7qLI2gDzxBAZ30JEhDfMes6sBWllfd_q6PvsPa-GhR2CZkb4NdSCG2Oonq0vuOf4dw5SA"}], "types": ["point_of_interest", "establishment"], "reference": "CmRRAAAAChnEHb-rQXO0MDEe-UP6OcVCuEJVMohi_hI0hcDyVuskO_xwjdqvmp68jhIbVVlOSYUgjLxOGLaga5n3SKml9HPY6iYIcSfs3zlqKhyZGiceg7mzpXpf84wg14KKcIv5EhAaaRutMGZgzfdXkreNLteJGhRzxsQJpgDL-Jy0oX0W69xSvmWxZw", "name": "Masters Fine Art Conservation", "rating": 5, "id": "a462c2eef4e22ea319485ae7b84f3d20756cbdd1", "job_title": "Servomex", "place_id": "ChIJp8u2bZvAQIYRbosnWz6cVmY", "address": "1612 W Alabama St, Houston, TX 77006, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.3876169, 29.794149], "type": "Point"}, "properties": {"photos": [], "types": ["art_gallery", "point_of_interest", "establishment"], "reference": "CmRRAAAAE6wjRXLVSR1yQNRj5SujlKOA3GpGT_LfrYrB93P8vWXA9UBSwXa4S9W1b105QprisuomArhkHpWufi3ABA-1_smKs74acoacSiKPMjPvz8liStv6r8HAN1PQuXD68nHPEhAWa_ODfcLXDqmWRDvlapdPGhSbNc7eFq9rYMC6gpiptKq9jwkYEg", "name": "Whitten & Proctor Fine Art Conservation", "rating": "NA", "id": "883a8c5ef35ab28e1630235ad65a6b16506a67fa", "job_title": "Servomex", "place_id": "ChIJ8YuXE6K4QIYRn1SF1hazFEw", "address": "1236 Studewood St, Houston, TX 77008, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.3858767, 29.7300997], "type": "Point"}, "properties": {"photos": [], "types": ["point_of_interest", "establishment"], "reference": "CmRSAAAAYXXqFZvGFxiee7HQRgZN1K9wwf0rXtSOEkEsgoMs_4MNKX3TBsZNynjx_ZWa4z1iDc_3OBxJjRAP1iGW2rTFXd_EyYzqg2cF-JGc2127FfUxnxbgQST1LX5KeaiGGQzUEhAKbwMNJ3t0PpnZp6bD-vUPGhTA2ojaLLQbRYr3fsU_txYJOGjM2Q", "name": "St Mark Fine Arts Conservation", "rating": 5, "id": "ea2d4bac6d74716b33f456dff3aae0cc0b43cca3", "job_title": "Servomex", "place_id": "ChIJKbDEoXm_QIYRcRFBlp0dE8A", "address": "4901 Main St, Houston, TX 77002, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.483218, 29.7482286], "type": "Point"}, "properties": {"photos": [], "types": ["point_of_interest", "establishment"], "reference": "CmRRAAAA1t0Tnv31tm9VP5SFntWQytchgOsV6iNfChm_StfUrGivEH8ngLdl0ZSGbLUqTQ6Y161T723heFu8z-dWdq3PcAf-zXD3mtvEHEASdiMDo1Jz6bM0zUJSiuc5lThctMKKEhCQFDaPU4s4PrrwcYqz6tNEGhTAjlI91i6EF12CBFqTKwJxoBbRDQ", "name": "The Nature Conservancy", "rating": "NA", "id": "90af6fb9fb926dde9f7103577cebc4150bbb1dec", "job_title": "Servomex", "place_id": "ChIJq-m4EX3AQIYRJkn4Lhccp2E", "address": "1800 Augusta Dr #240, Houston, TX 77057, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.42318089999999, 29.7345943], "type": "Point"}, "properties": {"photos": [{"width": 750, "height": 437, "html_attributions": ["<a href=\"https://maps.google.com/maps/contrib/106788706324997826205/photos\">Erika</a>"], "photo_reference": "CoQBdwAAAMMS8a7TtUPOYPQMTFpPLLLCUFt9OpXvzsgRvGBKSBYrO5bntnJLTuvSfGNgKKgAnGoklqCvicbW-ymMNQfbbVz4OvpCQ7u8_f1U8LU1j1UbGcBWPwyw0fpD44WL350_O2xv1MYr_dZ_bxgopClhk46YT7a4Zf-t-MiYdNagi3YnEhDzUaW-nDN5_nHqKV9ENwypGhTOrYoNj_yWzDSL_jyYN_JX419NIA"}], "types": ["point_of_interest", "establishment"], "reference": "CmRRAAAA9peLbCGptjfACu8REFcn1FMJ2REzdIkSsnt7EoAChcGTZ3Z3ErApHsTA1J9otv5A_E1ZoJYZTtheE_sdh2PO9mu5dpCe8PWq7vGscCpdZBEdTBMUQmNtkt-YBS4Ut31nEhBhHA7qa2n-Duqj5nGRHSADGhScMS_c-dHsztnv6nNrk3iZi6oPpA", "name": "Student Conservation Association", "rating": "NA", "id": "1c5ea7722fc0d99e9f7dfca55f5d9078224d51d3", "job_title": "Servomex", "place_id": "ChIJQcqBXfDAQIYRErawO-goGj4", "address": "2990 Richmond Ave Suite #400, Houston, TX 77098, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-96.038102, 30.055621], "type": "Point"}, "properties": {"photos": [{"width": 984, "height": 985, "html_attributions": ["<a href=\"https://maps.google.com/maps/contrib/110279808588468038448/photos\">Peckerwood Garden Conservation Foundation</a>"], "photo_reference": "CoQBdwAAAOX26vATz1_ZMTO1mV38fcpiH5VGeAb6r5aQvWDtK2qlwm2zDmRgBkFguCcy-4-PNYb5b8XU-S6oaEWD1Z_DAEyFUSSdRs1d31VjyI7meXGjZ924NiLJQGHttDe22_bHDyEph2JQm0JIB0RvpqrMI85wXzNXq2FSkwBD5iQrBIFqEhDrcEdpUojA4MjHoX9A4uJcGhTgnystSwiX_lRsKsnyBW90I5_TZQ"}], "types": ["park", "point_of_interest", "establishment"], "reference": "CmRRAAAALDmrmkNrvbK0k_svWrGJISWdhNgfZFfb9t8TgZ662G-NfQTA131hF15q8fvqN7BzQuBdNl8ZzHLqqFwJGyozsokiu0y-pTQlY1CQg7Tt2vZSDMvDIW1RqFBSSV74LZyUEhAgsJLcLXbZg1d3eZOBDs6OGhQ-z1uM7GjniK87QZLXIkEU3NO9YQ", "name": "Peckerwood Garden Conservation Foundation", "rating": "NA", "id": "e618a4c618cd67ce4f5fdc165f640220ab3b53b2", "job_title": "Servomex", "place_id": "ChIJmUR7pvHKRoYRIIl0o73bPGE", "address": "20559 Fm 359 Rd, Pine Island, TX 77445, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.64386449999999, 29.7515036], "type": "Point"}, "properties": {"photos": [], "types": ["point_of_interest", "establishment"], "reference": "CmRRAAAAKJs0Ts7OgrJmqYOH_AXr9tdUg5z77PBQCp7x_BWTIW3LrOcwGtRnAhcLx3ZNKAl-UPZyVNwZC5qfZNa-M3f8hzlaCUa_pNBfXoCkDqUNG72NYTnMB7pZMus1xTXvxVezEhAcMrJTfmhCKF8Jpt1J2cOhGhSgYFzsFHAzAQMLz1TbnyOBiLlWiw", "name": "H2O Conservation Technology", "rating": "NA", "id": "30c07988ef8dfc62dac712b9d587daa4a36f2539", "job_title": "Servomex", "place_id": "ChIJIWZRKeHKQIYRXxta3wOMGGc", "address": "1725 Hwy 6, Houston, TX 77077, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.5705632, 29.7714443], "type": "Point"}, "properties": {"photos": [{"width": 3024, "height": 4032, "html_attributions": ["<a href=\"https://maps.google.com/maps/contrib/108143329814504597326/photos\">State from Jake farm</a>"], "photo_reference": "CoQBdwAAAPphpKaDTW6N-McPFhYkun-s4FMTnuYjGUBUi-zkGgVc8ne4coZKvXSDalHOsIAm0tGsKYjgAWAtKPakJ6rS4rVLo8sBiHyVxuFAtzK8w5nC9j9fVE60iHM6lU4ZahPvkCAh738iolnzDxwc0PZv_iVLrb5HJuosx0Wf4kY65Gb0EhAlYVt037ok0PTK73gEHcsIGhQJSuKzqZu1g_xTVwmYxwx5LmUimg"}], "types": ["park", "point_of_interest", "establishment"], "reference": "CmRSAAAA_AQ6Ic_4TyGNtF2zwJLSpGTCuwWSoykH5iZLA85Y_ea4S_H-txjp18VXV7vwNfqoPrY95JNNh45kvsswS_RvvV2bePdiOaNsHEigDKhpiRs4GIaZFXaMzqkUQkcMHKY5EhBtew9LKJqpkpzmoHZABfSQGhSoUH40_vUK_xTUT3slyHbXFBl3XQ", "name": "Houston Audubon Society", "rating": 5, "id": "050a5458d86bdd1cee7b09678bd6256d0a20a73e", "job_title": "Servomex", "place_id": "ChIJlQOxwVDbQIYR2uX_TZl0TYc", "address": "440 Wilchester Blvd, Houston, TX 77079, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.56820189999999, 29.770778], "type": "Point"}, "properties": {"photos": [{"width": 1800, "height": 1200, "html_attributions": ["<a href=\"https://maps.google.com/maps/contrib/108765250995932379967/photos\">Audubon Docent Guild</a>"], "photo_reference": "CoQBdwAAALA5IO8q2MrGB5p502L2U-zMqNky2VOtL6M_nxKq3m5j0ZsY0SkC3QAtn_vNaZwEI2xDpAdCIid-8ZRyXTD0nsDg_20EZ_MfJIXkmpmX2U4vV4_xnwv_HZmgVVSCI4a2LNECNgUocBH5JvlooqbvmNJ6h1-zGIemxtqkAz-9ffR5EhDDT2pHWLdCTvUjZsMUmRaFGhQw75U4S-c5joPwQNzjKau4-I615g"}], "types": ["park", "point_of_interest", "establishment"], "reference": "CmRSAAAALj3Wpb7Y-Gqpe0y6x215Z4zGwIPNZbh2HdWWLvqSicmYXE9ZdY5KyRlXsy31bScW2IhhSDuTo8Y5ZDMFKgWJkSnudSq87P6zCm3K7ovJImT7uTmjkvRzbG3NY6WPM5-iEhAAxL2lGi3PKC62fCT9EYi6GhTxVNlHbe34vL4Xxz_q_232QPoLTg", "name": "Audubon Docent Guild", "rating": 5, "id": "7ddd5daf76cc4979e2ba6b062322d1c77d5d1c07", "job_title": "Servomex", "place_id": "ChIJI9XyNFHbQIYRtwHb8EtTpeU", "address": "440 Wilchester Blvd, Houston, TX 77079, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.44932349999999, 29.7803218], "type": "Point"}, "properties": {"photos": [], "types": ["point_of_interest", "establishment"], "reference": "CmRSAAAATtXnwhxH-KwFS20p58w1wqGgXBvivxNMRf2F2GZh8dO_hCBg5ag5htetFwyiNLxe-_aQjrp4mQ-ypzen5Rb-UWWKf0FBAVENZPbXPxa6Se8g7rZm9C1W99Bmdh7MNRqoEhC89xie9j2QRigMye7iVmK0GhTkpoiRJ50XnWmYg7whjxGML3MgRw", "name": "Coastal Conservation Association-Tx", "rating": 3, "id": "7258b034e119f31e82320bca6e72781ee9f79d75", "job_title": "Ccmp-Capital-Advisors", "place_id": "ChIJcekacM_GQIYRPzL13cgQrPk", "address": "6919 Portwest Dr #100, Houston, TX 77024, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.47039, 29.655454], "type": "Point"}, "properties": {"photos": [{"width": 5312, "height": 2988, "html_attributions": ["<a href=\"https://maps.google.com/maps/contrib/101184977609161362375/photos\">aug4</a>"], "photo_reference": "CoQBdwAAACGsNuS3-NCvP6Ti5d15PfDCIDWq5JJrrhJOsQnLg76JfNJZhSp2IuecMAPP6_x2RPXojKbRjORtmicb4tosNw0NQjGPGhNqk03DGD-AWiKiui0pmefH0dA80vcecq9fkZ0EpvUGzVgEjpBORC2daKqGDZIs4uVVNAm3dTAwcYepEhBV8z3pbc1Adc5TGPFRJ4y7GhQ19bWvvvPfNeQ41YscJ_xm9wPGaw"}], "types": ["park", "point_of_interest", "establishment"], "reference": "CmRRAAAATA6I_3QIlHrm8kF9LydgVpizdHD9wuLryNL77kQynCBEM2OPSAVAwDuYrGV1h71-uDi-tvKsnrEu-97m_848fDo8cf28CeNL4OLUirUwJ0CqsecQYlJZeI-pzpUnPxJmEhD7Lrq0jmqGDdnjTRLviPyyGhTiVfQDvCLTzE0ngXFneNtrReYpyw", "name": "Willow Waterhole Greenspace", "rating": 4.3, "id": "0127506e8071350c2d48f0ca56e939045297a0f4", "job_title": "Ccmp-Capital-Advisors", "place_id": "ChIJR6_2zTzqQIYRsA7wExgfDWs", "address": "S Willow Dr, Houston, TX 77035, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.4003322, 29.7388505], "type": "Point"}, "properties": {"photos": [{"width": 1136, "height": 640, "html_attributions": ["<a href=\"https://maps.google.com/maps/contrib/117056878997299689379/photos\">Marisol Brown</a>"], "photo_reference": "CoQBdwAAALCO93xoXatc-_DpmSp_8RPSW2MFpJHWPfb4Jn2VYKyQmydpDNKxjb4aZyAw1I6lTGWnw6KDE-bI-l-poc_76Sf2rggsKVOT0apn_OXTut9Jtq24NWAjWPFgWznI5NIdK3ddlTKkVt4PhsdAnkUaIfoyVE7TuoW2jHhb_J4b1-ddEhA5sg010kM8vE3JIbpSEa4ZGhQjwL2qdZJmd4uuLmBlZthk5S-OHA"}], "types": ["point_of_interest", "establishment"], "reference": "CmRRAAAARttvomwXdzSY1z5fuhUSijOgvIJZrdpaDJkWa8lWzFfeJX3V4Dgv8SFnPvgMVcZj9spL2GxIo0s5TLpDzducUcFcJBeA1BNnMe2Vi87GrilV46v1JXmqL1QqPAZDadhPEhDwpnm8IZJUrbS92JESSIAcGhSTJgAltYmM07Hk1y3JRQrBz1oqTw", "name": "Masters Fine Art Conservation", "rating": 5, "id": "a462c2eef4e22ea319485ae7b84f3d20756cbdd1", "job_title": "Ccmp-Capital-Advisors", "place_id": "ChIJp8u2bZvAQIYRbosnWz6cVmY", "address": "1612 W Alabama St, Houston, TX 77006, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.3876169, 29.794149], "type": "Point"}, "properties": {"photos": [], "types": ["art_gallery", "point_of_interest", "establishment"], "reference": "CmRRAAAAbx-3szhvyyTCGtAmfs-OkOrjETYK1J--qIM3lHXZ_2-fFLHlYlBa-JC7snVuLnECHOnkukJCW7XrMlc9I9-oAWaRK6AKMSMecRvdKh3YgjrBp1CJfEV80gOjye03UHNDEhBBMNtv-PltNQISV9eeHIQDGhRbXPUgNlrHoh-tSXt4XNM1Wa12Yw", "name": "Whitten & Proctor Fine Art Conservation", "rating": "NA", "id": "883a8c5ef35ab28e1630235ad65a6b16506a67fa", "job_title": "Ccmp-Capital-Advisors", "place_id": "ChIJ8YuXE6K4QIYRn1SF1hazFEw", "address": "1236 Studewood St, Houston, TX 77008, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.3858767, 29.7300997], "type": "Point"}, "properties": {"photos": [], "types": ["point_of_interest", "establishment"], "reference": "CmRSAAAAdDI07HLCIoDf2_DIZCfCKKLzdU0ZUauUsnTnj1C62LnVK3eyne333H5DmAl1INrUP20nyuRjc3w-UwmWQskE9_aF-waVscjLdu5qT65XzVwC96A7CN0dQZIa0MviI5YIEhBper5RckqzE-rl_d-PpgPPGhQtJpgyXqfWbha4o2g5TA5hxQgyWg", "name": "St Mark Fine Arts Conservation", "rating": 5, "id": "ea2d4bac6d74716b33f456dff3aae0cc0b43cca3", "job_title": "Ccmp-Capital-Advisors", "place_id": "ChIJKbDEoXm_QIYRcRFBlp0dE8A", "address": "4901 Main St, Houston, TX 77002, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.483218, 29.7482286], "type": "Point"}, "properties": {"photos": [], "types": ["point_of_interest", "establishment"], "reference": "CmRRAAAA24WTzOrVuXC0o33U6qJmY0wpeDunW2Igbe5h0b1rgHM3g0NDna8Owy2pCkhSzEStxyKXiu_Y7vg1bcYAU3y1Mdl5oQl3qK1eAe8flc84p4JLTFCF2Z0rHIBi_TSl5KIxEhAzaBYOqQP2nHxdAYfUhMVgGhSUbJzXQBtPxZ7JSg9z00Jsx5cZvw", "name": "The Nature Conservancy", "rating": "NA", "id": "90af6fb9fb926dde9f7103577cebc4150bbb1dec", "job_title": "Ccmp-Capital-Advisors", "place_id": "ChIJq-m4EX3AQIYRJkn4Lhccp2E", "address": "1800 Augusta Dr #240, Houston, TX 77057, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.42318089999999, 29.7345943], "type": "Point"}, "properties": {"photos": [{"width": 750, "height": 437, "html_attributions": ["<a href=\"https://maps.google.com/maps/contrib/106788706324997826205/photos\">Erika</a>"], "photo_reference": "CoQBdwAAAMOAiwLfBj34AqYedCyGGZoYeEtO_B_d3q2smGMJ62auIyNPw2iN2dLDV02XpIRY_BcfhpKF52CGUa6qndCXe3QbgJe0Hy2Ms3W_fbgEnaAvMBsSwEI0REZFNKGfSn1gmPrc4lKeo2wGB-HcuNWQI5hf_dmGC9e0038mprGskGVSEhBBPjzAXIGPhP0ld-BKCzu7GhTLE-AvaQ5-fk7UUMOA182Z7Yi4Vw"}], "types": ["point_of_interest", "establishment"], "reference": "CmRRAAAA8APNC563OsVgHZYG_HXHtJbcrtR1l0BtzEtH_qkImxR4PBfoHYHFL1sk_dogMWcLJMyu_PgxUiD9XzZdS1JNvEMIXzwucxabPNMtyZcXCa_GwPR2vm4MTrnQnUKeEVjYEhBdwXyuibHPrj0pyUNiPzZlGhSyqnakW1tfwxNt4DdALoO0qNoxKg", "name": "Student Conservation Association", "rating": "NA", "id": "1c5ea7722fc0d99e9f7dfca55f5d9078224d51d3", "job_title": "Ccmp-Capital-Advisors", "place_id": "ChIJQcqBXfDAQIYRErawO-goGj4", "address": "2990 Richmond Ave Suite #400, Houston, TX 77098, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-96.038102, 30.055621], "type": "Point"}, "properties": {"photos": [{"width": 984, "height": 985, "html_attributions": ["<a href=\"https://maps.google.com/maps/contrib/110279808588468038448/photos\">Peckerwood Garden Conservation Foundation</a>"], "photo_reference": "CoQBdwAAALcq6v_7QL3-q41cvO8OF97cqLvosbhKLulDZcKNftuMAt_8Yz4AvSLcBMls1MV8l8dgQGe3jQbOfwRyw2y2IaSPxmfeHcQ0XSIXwsPUpFSKNR0fTc6wdnx5IDZJKTV30KCf7JbjSD3TW35RQkMZahDQ6JVnK9nHwZfBpzW5s0GwEhBfp4nKOUQc93l0-3ClBNzaGhQg7OxHseTTSRCbpD1j6rkhfllayg"}], "types": ["park", "point_of_interest", "establishment"], "reference": "CmRRAAAASiMv3TOQm3aj8uE9MMJSBNrngnSJP3wroXa64YQBobwPVgWghvOCg8Vtn3bzl6eWvng5qkoaqDnjSMk1Ip88oh1djoQkB4ZdHoX7Pz-mXJvfyBcbbhig-jBwNLanvdcFEhAca6kIiSI-kOEoTL9cHI2XGhQqk6vKv_gE9o7X5MDTLIlhPulMJQ", "name": "Peckerwood Garden Conservation Foundation", "rating": "NA", "id": "e618a4c618cd67ce4f5fdc165f640220ab3b53b2", "job_title": "Ccmp-Capital-Advisors", "place_id": "ChIJmUR7pvHKRoYRIIl0o73bPGE", "address": "20559 Fm 359 Rd, Pine Island, TX 77445, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.64386449999999, 29.7515036], "type": "Point"}, "properties": {"photos": [], "types": ["point_of_interest", "establishment"], "reference": "CmRRAAAAJIiB-st2kV8XDb291R0_Quy0nJ_EQEWDv7PrapccocszkZRBqO0gCwb2BUXJ2O_l-cKb8j1DUFGgh1mwbE8xn9uAJDrE-n_FFBeypWZ7BlKlFWK8LfpJ955QZQ0o5sogEhAVz4C8xnnTsxYWIz-5reLEGhR-BY5zpIY9hUi8w1lJLO3SYKMVHw", "name": "H2O Conservation Technology", "rating": "NA", "id": "30c07988ef8dfc62dac712b9d587daa4a36f2539", "job_title": "Ccmp-Capital-Advisors", "place_id": "ChIJIWZRKeHKQIYRXxta3wOMGGc", "address": "1725 Hwy 6, Houston, TX 77077, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.5705632, 29.7714443], "type": "Point"}, "properties": {"photos": [{"width": 3024, "height": 4032, "html_attributions": ["<a href=\"https://maps.google.com/maps/contrib/108143329814504597326/photos\">State from Jake farm</a>"], "photo_reference": "CoQBdwAAAIJg9zA0UdzAQ8XDXO8vXgiahZClc2FIZCtp_vu3ltsDrQjTpWxqTxuFLKCtLu7CTr47OT0wxlZ-ee7MP_bORmN995TmzTnPYPRyBquAax1AKGs3xTpTilB-jfico_ZH2j9_z7Duf-d47wzLl_vk2-O6YxL-_4Rcc8Sj-1Kp94R4EhBpn6GCaGl6vSCjq80QaeFGGhRSyH4pc-YB5X8_IlJnSjDrmR7y2g"}], "types": ["park", "point_of_interest", "establishment"], "reference": "CmRSAAAA-hA0nJmyyGvCqSxZpecJvyZR_u9Ut8PlIpu4xdTWE25NE8mRJU-feIBCeopAXlePuxF-K3QyThIJp809eA-TNZX1N2W22ZRKEn3JM4WR9n3CSKH9jfMTdL6i9w2RvPRREhD8lrEpOAZOmL5uulhO0XLiGhSTHyh_1FykUH-3vF4PNq-QC-IsfQ", "name": "Houston Audubon Society", "rating": 5, "id": "050a5458d86bdd1cee7b09678bd6256d0a20a73e", "job_title": "Ccmp-Capital-Advisors", "place_id": "ChIJlQOxwVDbQIYR2uX_TZl0TYc", "address": "440 Wilchester Blvd, Houston, TX 77079, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.56820189999999, 29.770778], "type": "Point"}, "properties": {"photos": [{"width": 1800, "height": 1200, "html_attributions": ["<a href=\"https://maps.google.com/maps/contrib/108765250995932379967/photos\">Audubon Docent Guild</a>"], "photo_reference": "CoQBdwAAADoq_nWtPm5XGD4ZdMAF2q9GM3e68fcDOk0y3oC750oFMyyA3f9FgoPFvkSY5rL2lznDvGygO995uqfp1o5QbM7n_nwPWI9sLK6HYmsHnFLr9jhyq6Zg4Nyh6Rr_sBS7Wd3BNdchbGPMep5TLf4oxDPcrU6-23EFDGox7sx0XcDeEhDHz71iLjhXlQJSqPNcVdurGhSOz0RXYz7TE1nsLnIS99_NPU3CDw"}], "types": ["park", "point_of_interest", "establishment"], "reference": "CmRSAAAAAMx1ySBhE4bAw6qbzQNGgNRM8FVLN0UKyd0HhgLWz2nzNw2U7I00OvcbfA7MlsFZUYNyqJh6hH0o6TrmVtguVAuRw-Ih7Ft4nvCtRSlrpVbe8p-9NrjoEjKeFzyLD9OeEhBpTkloY6U63DeEfno6QJYOGhSesS1Bwlxw92o6V7pddhWGAUhfjw", "name": "Audubon Docent Guild", "rating": 5, "id": "7ddd5daf76cc4979e2ba6b062322d1c77d5d1c07", "job_title": "Ccmp-Capital-Advisors", "place_id": "ChIJI9XyNFHbQIYRtwHb8EtTpeU", "address": "440 Wilchester Blvd, Houston, TX 77079, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.44932349999999, 29.7803218], "type": "Point"}, "properties": {"photos": [], "types": ["point_of_interest", "establishment"], "reference": "CmRSAAAAk-EYR88Z7dN6F_Twv8S3vD9BomMzs0pu5asxK552knY38S1IwBSNBQoLTkjn0d1Ij92O3JQx9pnj5-H8xndbOkWOQHjeeaE_YeQkf4gXptkv1FVJw6R9J7tB6gQTMZ7UEhBvMiXZxJ-Uy_1HIpEEPYsIGhS5EMvvWxhLSOqibX4YxH6PISgW8A", "name": "Coastal Conservation Association-Tx", "rating": 3, "id": "7258b034e119f31e82320bca6e72781ee9f79d75", "job_title": "La-Quinta-Inns-&-Suites", "place_id": "ChIJcekacM_GQIYRPzL13cgQrPk", "address": "6919 Portwest Dr #100, Houston, TX 77024, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.47039, 29.655454], "type": "Point"}, "properties": {"photos": [{"width": 5312, "height": 2988, "html_attributions": ["<a href=\"https://maps.google.com/maps/contrib/101184977609161362375/photos\">aug4</a>"], "photo_reference": "CoQBdwAAAIakYfjJVidSoFHuplr-xIE-bOThsKs0aM5Kl5cCwSGo00YgqAnz1ip-yNL-BRJhfLyu6svGZ3em15s0tGGU5DXL9nDQw-Q27X5bZCYh74jTWTzznjd0i87PQmqztQu15N5lsphA7oo9XCZZ8lgaQSIzuSBZwtbYSkpYO5lX4paOEhBHk7v7HhbaKEkQaTUR6UGsGhRc466liFVbBfZfWHaUCa6IJjRPqQ"}], "types": ["park", "point_of_interest", "establishment"], "reference": "CmRRAAAA0aAeohDVfDc5gAuvW0zQBbQvdA1bk0WXRJbYexaH8A9LBzkeUCpQ0A76hr8720IqJ7z7_Ky6ktHnu8JA60tYeGR_bQe0TKmafscBZgN2r3NqI4wXOyhySIY6XqDbCHMlEhAeOzvzMr-Iw6SXoBisXeqVGhS76KwpbKgQCKOQszNdYkiolAjYsA", "name": "Willow Waterhole Greenspace", "rating": 4.3, "id": "0127506e8071350c2d48f0ca56e939045297a0f4", "job_title": "La-Quinta-Inns-&-Suites", "place_id": "ChIJR6_2zTzqQIYRsA7wExgfDWs", "address": "S Willow Dr, Houston, TX 77035, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.4003322, 29.7388505], "type": "Point"}, "properties": {"photos": [{"width": 1136, "height": 640, "html_attributions": ["<a href=\"https://maps.google.com/maps/contrib/117056878997299689379/photos\">Marisol Brown</a>"], "photo_reference": "CoQBdwAAAP2QWbCpgrSOwrYCVlpNOmC6mevas4Zd891lgVIcqvVvYBgAS_1svl98H7XIrGPd10VZRPZYtwBg2xGNQ1kxv5IlG92X7Wdn5-r8KTlLpq2ZTDwrM7K5qr49Sf4JdDu14uxHK_zzy2Blz7uprxxyvVOffZinLKHo_Ocx4zQuy027EhDqy4LJ_9-qDZ9aDRYD3ACNGhS5biVyHaW6_wXmsOoAqM4ayCbidw"}], "types": ["point_of_interest", "establishment"], "reference": "CmRRAAAA_QpFI5O03VxQmKUWZJ9MvHufhYUQEkrwArCKNLM1HuRM3xxXBsDy5Sx7xYufjegpYNbbDIaQbkNa8a30i7U3gUBUwJnN4TKrj7td5Z61rpKgri3V9I8p0gaznu3KY7W7EhBlI-u0gnBiKRAn2oEVa2tQGhQ-kVMV0tWW57gqYOhzdKIf5aaPGQ", "name": "Masters Fine Art Conservation", "rating": 5, "id": "a462c2eef4e22ea319485ae7b84f3d20756cbdd1", "job_title": "La-Quinta-Inns-&-Suites", "place_id": "ChIJp8u2bZvAQIYRbosnWz6cVmY", "address": "1612 W Alabama St, Houston, TX 77006, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.3876169, 29.794149], "type": "Point"}, "properties": {"photos": [], "types": ["art_gallery", "point_of_interest", "establishment"], "reference": "CmRRAAAA_acPic36G4jsG55PgSmKrovTqQwmLia2W9XNk_2eFjViwxC-O81o3BbVoCsZm-ushP133SQEP9GxZKrqwDJfaFq7zI8fTOlYRrH0UL6YwvtRHlA95XnyO23MAA00rNimEhCv4CWSb35S9K4OJfcFVNFuGhQWwd5B5RHm2rDwoyjCShh9YuUUEQ", "name": "Whitten & Proctor Fine Art Conservation", "rating": "NA", "id": "883a8c5ef35ab28e1630235ad65a6b16506a67fa", "job_title": "La-Quinta-Inns-&-Suites", "place_id": "ChIJ8YuXE6K4QIYRn1SF1hazFEw", "address": "1236 Studewood St, Houston, TX 77008, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.3858767, 29.7300997], "type": "Point"}, "properties": {"photos": [], "types": ["point_of_interest", "establishment"], "reference": "CmRSAAAAnnBODLW_-M12AZK6tbcs1qIq1SVpescKaRw2AN_j23McS_I5QUqkNsko3NtryRQ0qKdP6Dy-4FTi0lp1AgtXDRzxQS7MeeqMsYrn5K3TMj7zE8ndVxLZRnHLZjGt4zBtEhBGa5rFxdSu_BwtUuBv_CWUGhQ6uV3Ey1bMJhoEaivo8hWzucPLsA", "name": "St Mark Fine Arts Conservation", "rating": 5, "id": "ea2d4bac6d74716b33f456dff3aae0cc0b43cca3", "job_title": "La-Quinta-Inns-&-Suites", "place_id": "ChIJKbDEoXm_QIYRcRFBlp0dE8A", "address": "4901 Main St, Houston, TX 77002, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.483218, 29.7482286], "type": "Point"}, "properties": {"photos": [], "types": ["point_of_interest", "establishment"], "reference": "CmRRAAAAhfug6NOdF2kyVMSU4vMMuWn0fFv7n3YE5DamMJU2AwoM0ynCJU3nSLMq9xK9sPVZVuUCDixl1IU3ZhvrxPlGsjGh8s_0POZ18C7Cs8Zb0YJNdM-DYGN2hgH4RnfAesywEhCSskphIMwwn8FQEcozEI2tGhR8rW0KMcxccovEPzFo7fnXxw8nWA", "name": "The Nature Conservancy", "rating": "NA", "id": "90af6fb9fb926dde9f7103577cebc4150bbb1dec", "job_title": "La-Quinta-Inns-&-Suites", "place_id": "ChIJq-m4EX3AQIYRJkn4Lhccp2E", "address": "1800 Augusta Dr #240, Houston, TX 77057, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.42318089999999, 29.7345943], "type": "Point"}, "properties": {"photos": [{"width": 750, "height": 437, "html_attributions": ["<a href=\"https://maps.google.com/maps/contrib/106788706324997826205/photos\">Erika</a>"], "photo_reference": "CoQBdwAAACLqnUDhYm07D4oCWUSmObOKcdNUq5MljN0m883Dz9TFuiexeCyiOpFZByu4WK7H1BRC-UjnNqKl3av5Wjjgj4MkGVDnPtocO6XCbrEP_UnQ5fuyZCJUjj4q8EHofxGlv6kAD7vrHmYdOqrPrQK2ESjMI4Zlxdfpw6yodepKpZnpEhAaK7svck2OvU3yBj5hFQH8GhSFMeWUkUQGL46aVLKuWNNg_ZtgjQ"}], "types": ["point_of_interest", "establishment"], "reference": "CmRRAAAAL_NHUMTWtcOz9z5f4LH7RVDiQr51ZentH7u5UtO76SMDvRMxex9V-XolGHZgbtjFNCqrdJ_TuBwHnTkAs1mjCkWYXEDp82SzF2j_pgYqEXpaKj4lscalp-CiP6ICaEl2EhAivAd87SzVxTUM4zZa_jS2GhQPbY3gUDuK16efZK4IXuynQf7yeQ", "name": "Student Conservation Association", "rating": "NA", "id": "1c5ea7722fc0d99e9f7dfca55f5d9078224d51d3", "job_title": "La-Quinta-Inns-&-Suites", "place_id": "ChIJQcqBXfDAQIYRErawO-goGj4", "address": "2990 Richmond Ave Suite #400, Houston, TX 77098, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-96.038102, 30.055621], "type": "Point"}, "properties": {"photos": [{"width": 984, "height": 985, "html_attributions": ["<a href=\"https://maps.google.com/maps/contrib/110279808588468038448/photos\">Peckerwood Garden Conservation Foundation</a>"], "photo_reference": "CoQBdwAAALUz6OBX1tyyOMuw42_fgRIlYIW-XUl62vUh697ErxT0vPe2nVnYE5CdQWk73sBn0vgm_6CdYRcUZHxIeOmvIoVPAgz9PNprsB8Bwv-VgsE48Ko661e5qIHCikOR8OBeuLnDXz9wltHBoKAbMuF7uS2u7t2fMVlvovk8HLxPCICqEhAc6yz3bODfB0K2KJZpIZAHGhT0-bGjnw-fMR8IFPIqzxQ1BLOMeQ"}], "types": ["park", "point_of_interest", "establishment"], "reference": "CmRRAAAAgpnS0XdnVaSZZiDEjaNz-C4Sd0hdqlWXjh2eXqD4HxPPEbeg_22M_vvDB9JlWffYDaIbCQhxy_Im8Cso5PlvFoN8lKxYndRS-t0rzb3JJvAydw-xHzxq9JWz3raLE-bZEhDzBXdp9zI-o1tFYAV_L8qdGhSgjvGW4dTUv0VQuHa5D8CehKwCng", "name": "Peckerwood Garden Conservation Foundation", "rating": "NA", "id": "e618a4c618cd67ce4f5fdc165f640220ab3b53b2", "job_title": "La-Quinta-Inns-&-Suites", "place_id": "ChIJmUR7pvHKRoYRIIl0o73bPGE", "address": "20559 Fm 359 Rd, Pine Island, TX 77445, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.64386449999999, 29.7515036], "type": "Point"}, "properties": {"photos": [], "types": ["point_of_interest", "establishment"], "reference": "CmRRAAAAnvriVSY03wovlRbdx4tYCD3J-78aX9oUEtJ-Zxq_Up-uT6HgAulwmVzRVrLYD2XZjPujYoEXaBb8Rl3_UygMA_i6oCOuy4T9Ac1VNnuxy_-5oA8kAlV-9T5VP7azI8G-EhBNtrczX19XcnUwct5_JRkHGhTB2ilxFev1Jgefs-WEIcD05ko7rw", "name": "H2O Conservation Technology", "rating": "NA", "id": "30c07988ef8dfc62dac712b9d587daa4a36f2539", "job_title": "La-Quinta-Inns-&-Suites", "place_id": "ChIJIWZRKeHKQIYRXxta3wOMGGc", "address": "1725 Hwy 6, Houston, TX 77077, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.5705632, 29.7714443], "type": "Point"}, "properties": {"photos": [{"width": 3024, "height": 4032, "html_attributions": ["<a href=\"https://maps.google.com/maps/contrib/108143329814504597326/photos\">State from Jake farm</a>"], "photo_reference": "CoQBdwAAAGhawUAWBiNna8QuBJ0oMXokuk_fEsXhYI8l4v0DL7IiREELbujVfppDEKrg6GlmghsoHJyyx--pjmHoPekNcFF_xWy5v-USeoxgS9cseLZzYOjV2-m2B3kE3d-Fbq3H0hrfWe0wtrveNlsQ9sACSvOnANtPorAf2eVdmPpH2VVbEhCvVzVrWEBAzMU_c0MPT5V6GhRghw7dZVruptWyYGkV_RiZxdGUIQ"}], "types": ["park", "point_of_interest", "establishment"], "reference": "CmRSAAAAzFHRBetEVu70S3EM9hmhoOFD6GzZ15LLGpm4_U9MpIejddmtSoUMtMKQO0lxEbVfgMsqCNldPRWZR3os33MI0G2aI0KDc_t17vtnsqeVNXwEHusIr1PZnDAWmmbSmBLAEhAg0dwer8xxTYvgFqgoZXR6GhTPmk0VVHhTEycXJaBZAZgJ7ZE0eg", "name": "Houston Audubon Society", "rating": 5, "id": "050a5458d86bdd1cee7b09678bd6256d0a20a73e", "job_title": "La-Quinta-Inns-&-Suites", "place_id": "ChIJlQOxwVDbQIYR2uX_TZl0TYc", "address": "440 Wilchester Blvd, Houston, TX 77079, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.56820189999999, 29.770778], "type": "Point"}, "properties": {"photos": [{"width": 1800, "height": 1200, "html_attributions": ["<a href=\"https://maps.google.com/maps/contrib/108765250995932379967/photos\">Audubon Docent Guild</a>"], "photo_reference": "CoQBdwAAAI1-I6HYBgPoQGFGl3XlqH4G70RyB27-3c-01Ke1F4lPEi3wLV707Ea3B3moSIlkY-9ZcLAAfFuCrTuKf0jlyWs8DvFtBsFPSDH9E6kpA3mifdcCu72j9hsc54YOVa3tVEXEKJ-DgwStAvZ88o0D9gGmfpO4oB2IZRCPrvl-R-suEhD5uGLWj0r5RKLrFX7Liza9GhQWCkhfeJrHv2S2fYINRps4h4PekA"}], "types": ["park", "point_of_interest", "establishment"], "reference": "CmRSAAAAjNa6r6u_fWud51otLQbTZ9tT8C3svaXQtxbMd6vYy4rIn6u0ef9Z6ishXl2p16rfyJYa7QbNaWrb1awJGBBVpXfG08uA34ChiEDPVGUh4x_3StbSWrFHTntYfAJBTsfeEhBL0jrODyXRpP_9e07VNn3dGhS8QD9r8m5NfpiO6Y-JrAKcq1pfew", "name": "Audubon Docent Guild", "rating": 5, "id": "7ddd5daf76cc4979e2ba6b062322d1c77d5d1c07", "job_title": "La-Quinta-Inns-&-Suites", "place_id": "ChIJI9XyNFHbQIYRtwHb8EtTpeU", "address": "440 Wilchester Blvd, Houston, TX 77079, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.44932349999999, 29.7803218], "type": "Point"}, "properties": {"photos": [], "types": ["point_of_interest", "establishment"], "reference": "CmRSAAAAWp3qQZyXkSsfBd4x6vZ_M_04oHK6wq9SSB_wKuXfYG7bmCdhrxmH0VfGAJZm4b_vvl9NwNt-_v9yvJIMsUm5JoS9QpsYmDX1Qj55g1nyvgLIhPsJYiy9A6Bv1h1rKtxdEhDqNvP8mWO6i4_kzGOPlC2JGhTAFDPXcW5fVbKW6vVFtgb8Obi3HA", "name": "Coastal Conservation Association-Tx", "rating": 3, "id": "7258b034e119f31e82320bca6e72781ee9f79d75", "job_title": "Severn-Trent-Services", "place_id": "ChIJcekacM_GQIYRPzL13cgQrPk", "address": "6919 Portwest Dr #100, Houston, TX 77024, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.47039, 29.655454], "type": "Point"}, "properties": {"photos": [{"width": 5312, "height": 2988, "html_attributions": ["<a href=\"https://maps.google.com/maps/contrib/101184977609161362375/photos\">aug4</a>"], "photo_reference": "CoQBdwAAADazm5ptLtDoogjB8iaAkfW09JKL3Cow3TG10LkjSpfpCzZFlXihnBaqzKMH0bNSQhfx6Tz1u0_6SsCVsxMQH1Obnpn3ZovAJGQ8F-OJVGEwwchlKxhAoYpJOvPmi9fPlnoNBVBdS_uChFbhotUgtGJkh7_jH5sfZOouJrU4wgruEhCB_EM7AJWImNeCQqX6epI1GhQ33wCOAvVM-OhBJ7x2Dap5CyBfbg"}], "types": ["park", "point_of_interest", "establishment"], "reference": "CmRRAAAAAMsa0-KAbpA0uavK5jhtm_RmCU5iHzM-GsxUC4s676pLyhe9fUzRDOeu_GtD20w3Ka9gVE7OIwoaCuPaZrthCoatg-pNZ1VbLl1mnY7Sz6ZBeU6mOAzLTILqrbGc1aYNEhCb8ZlCG_CjPCjMhDIeEsO_GhTyl5bATi8CqGYAxWPIWxXGOqbPOA", "name": "Willow Waterhole Greenspace", "rating": 4.3, "id": "0127506e8071350c2d48f0ca56e939045297a0f4", "job_title": "Severn-Trent-Services", "place_id": "ChIJR6_2zTzqQIYRsA7wExgfDWs", "address": "S Willow Dr, Houston, TX 77035, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.4003322, 29.7388505], "type": "Point"}, "properties": {"photos": [{"width": 1136, "height": 640, "html_attributions": ["<a href=\"https://maps.google.com/maps/contrib/117056878997299689379/photos\">Marisol Brown</a>"], "photo_reference": "CoQBdwAAAEsLPdpSNxJbRtgnas6wjB_VnzPZ612k2TZncmOPWybIA2xQO8Rog6QR37BatgsRFlGPd_RZYoEUzTJ_RwgY6Gsq-NGzXLOQA2qB0XCIL0JBkeTMaU0oHIrF4S6uh4aIDdl0fYOmGT3-PG9vKMUfJ-kM5vl6UwGuWKhzhmy2l4M1EhBKQMammk-hri1fup0fQ083GhSkdTJrKINvZ4mOF2bvULddmbX4cw"}], "types": ["point_of_interest", "establishment"], "reference": "CmRRAAAAjKCAB55d8-ODfkvRqs0ToUh--Kayl7r3h8-ji0DBa5HEgF8xT4WK0jt3kTA7tcrQv_6uC27Oiqxv12g7H0cB9F9DeGonPL0y_eDqrW0e15v3yP0LAKQjsrlZYL3otPE6EhDf27Mgnk2boEr4XwWYtBmpGhTcbg2O5NGFsphPNS2Vmwa4HiFYTQ", "name": "Masters Fine Art Conservation", "rating": 5, "id": "a462c2eef4e22ea319485ae7b84f3d20756cbdd1", "job_title": "Severn-Trent-Services", "place_id": "ChIJp8u2bZvAQIYRbosnWz6cVmY", "address": "1612 W Alabama St, Houston, TX 77006, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.3876169, 29.794149], "type": "Point"}, "properties": {"photos": [], "types": ["art_gallery", "point_of_interest", "establishment"], "reference": "CmRRAAAASqRAaYNYgB8UJhoYoIaHD0DctYN2O0Ugn7cdfQ09HxorrdjDAIazfbm8zhALYzSS2_4juOZOYb_kme0oCsR0PUEA4mcyELxytx6HELOysyi5_DiLg57rhGLD2ksWKj_fEhB8n9nx_HAOu2d5H0776XW1GhQ0_G_90CO1xk2EF4hpHmCJndp-ow", "name": "Whitten & Proctor Fine Art Conservation", "rating": "NA", "id": "883a8c5ef35ab28e1630235ad65a6b16506a67fa", "job_title": "Severn-Trent-Services", "place_id": "ChIJ8YuXE6K4QIYRn1SF1hazFEw", "address": "1236 Studewood St, Houston, TX 77008, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.3858767, 29.7300997], "type": "Point"}, "properties": {"photos": [], "types": ["point_of_interest", "establishment"], "reference": "CmRSAAAAwe4jSnv7zbquJRW20LwO6iJ4E4xQ4OKwbvfnIw-rfradf968rQn-lF6aAocNCuI7cSS17Na7cSGlvSbauIZ0twp_0L6xr6j9VXGKHlIKrYjFrD5gfc95KP6SZqW7cSNfEhCny2JxAyJqZRLXt-bfvSyjGhS20GiNYJGQXhAin-eC4j6goMDluw", "name": "St Mark Fine Arts Conservation", "rating": 5, "id": "ea2d4bac6d74716b33f456dff3aae0cc0b43cca3", "job_title": "Severn-Trent-Services", "place_id": "ChIJKbDEoXm_QIYRcRFBlp0dE8A", "address": "4901 Main St, Houston, TX 77002, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.483218, 29.7482286], "type": "Point"}, "properties": {"photos": [], "types": ["point_of_interest", "establishment"], "reference": "CmRRAAAA9X6vl3XGa8uuSTRzeafwHMjInsppEhXbRiiAmDdwS8EWM4WH63MlmugIXUFght7aWu2u80Yta-XFPfHahE9Tlm5H34WZCaqMvxBk82OaY29k8XsA4pEWW0ScILQS6xo2EhDiSmfuD3SVRZT02xgSH3MlGhTAiskvZfVajVjCr56XEeFk5NTj3g", "name": "The Nature Conservancy", "rating": "NA", "id": "90af6fb9fb926dde9f7103577cebc4150bbb1dec", "job_title": "Severn-Trent-Services", "place_id": "ChIJq-m4EX3AQIYRJkn4Lhccp2E", "address": "1800 Augusta Dr #240, Houston, TX 77057, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.42318089999999, 29.7345943], "type": "Point"}, "properties": {"photos": [{"width": 750, "height": 437, "html_attributions": ["<a href=\"https://maps.google.com/maps/contrib/106788706324997826205/photos\">Erika</a>"], "photo_reference": "CoQBdwAAAIP6vhRAIAqSygI62Xc4ExYNXqL386du6GXkOWXPTIV_bwt6zezLx7f0iQRKchP-HA68Q80TfdGqlEpC3diYoTp7oZ6jE5jZUvQ435zT9C45ZEAcm_SOKps2awIV9t2-0qCQQABCu5S86gurk8fLse1Mh79NvYHS0gZkLjYo_9pFEhDg-GVi3i9zzVUCZPmrI9WaGhRrMBmNHPyg7_ek5-e_8G7zz5HzgQ"}], "types": ["point_of_interest", "establishment"], "reference": "CmRRAAAAzjV6oJKLp2m81yZVi2bgAm8O4kqU2oSCDdCWioGJOtWX1O5FrpXJCbVVHg6lKdBDhQjMhMUi7kV0QEqGowF7OzTtN7_sNf985dIzAhtzEl3zYeFvZ3D5pzFgso5tBj6kEhDNChUKGf1Z8vcuhmaQkFRpGhRF3iaZaaNjrCtBRfDbi-RNknt0FA", "name": "Student Conservation Association", "rating": "NA", "id": "1c5ea7722fc0d99e9f7dfca55f5d9078224d51d3", "job_title": "Severn-Trent-Services", "place_id": "ChIJQcqBXfDAQIYRErawO-goGj4", "address": "2990 Richmond Ave Suite #400, Houston, TX 77098, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-96.038102, 30.055621], "type": "Point"}, "properties": {"photos": [{"width": 984, "height": 985, "html_attributions": ["<a href=\"https://maps.google.com/maps/contrib/110279808588468038448/photos\">Peckerwood Garden Conservation Foundation</a>"], "photo_reference": "CoQBdwAAAHLomVnpTRdcRzbIO0V-iivI7edNMwluC0iEqXPMFMDF9OEI33eVw66ZsToceLl7i7NSMHKRDGb5Xh5OYo9H9WOfZWFq5J-leXichnUCHIrczuIXghnIUXHbUrgO-5LwCSp3Ua02MgH-apu-OYc3K0p3OLreTM4wdFrojewrjqF7EhDKNDelwDkiqcDkO8PjTtoNGhQxxAVWqMwwmMw0JkwEMu0BFVS9Rw"}], "types": ["park", "point_of_interest", "establishment"], "reference": "CmRRAAAAsHGJ4APbWG9Ui9CL7b4_H2B0-Uhh-MP7V_Stpdw9ABGjUP0_SMemAv8eOrdih-FXLzkmqOKs_sfJ_SThGQ5bWzQdhUMOn98CrnzWBeudCmDfzhY8PPKDml7iDjkTU-cjEhByKsOGBxqdrvNTHHENb4JTGhTTfwX4kxtI5VYl6dRy5mLsLgBWuQ", "name": "Peckerwood Garden Conservation Foundation", "rating": "NA", "id": "e618a4c618cd67ce4f5fdc165f640220ab3b53b2", "job_title": "Severn-Trent-Services", "place_id": "ChIJmUR7pvHKRoYRIIl0o73bPGE", "address": "20559 Fm 359 Rd, Pine Island, TX 77445, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.64386449999999, 29.7515036], "type": "Point"}, "properties": {"photos": [], "types": ["point_of_interest", "establishment"], "reference": "CmRRAAAATxDP-DXXIEFhvQdi3VD_B-TIRKbgFOLc5Ka08ljrqSHNB68qcVIpTyciGBQQTfMI2CFJJAEilBtdxxvlVc4g0dTJos7MqGsfU3b2sYDSLbk5_sxPyV75RsLVjwTXYW5REhA7bC0FeRls3D60XtLYTK_HGhQn_QkBnda4B8-RsqBE9dWSp5Py8g", "name": "H2O Conservation Technology", "rating": "NA", "id": "30c07988ef8dfc62dac712b9d587daa4a36f2539", "job_title": "Severn-Trent-Services", "place_id": "ChIJIWZRKeHKQIYRXxta3wOMGGc", "address": "1725 Hwy 6, Houston, TX 77077, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.5705632, 29.7714443], "type": "Point"}, "properties": {"photos": [{"width": 3024, "height": 4032, "html_attributions": ["<a href=\"https://maps.google.com/maps/contrib/108143329814504597326/photos\">State from Jake farm</a>"], "photo_reference": "CoQBdwAAAMnouDafCjOOmHH_ZEh3QQ9fVwUxKEvqQR81Atk0-niBBG-Hoaa0Wkfcy5Le7Z055ybcpV9jV0ir6dzj4Kt2dc0whmdzmChumWcnVK40zrxa0D4DAlSgpTQMKlBqJ6ZFNUv8lQj2rL1hr-cE6fovJgZZQKFesCRAj31CLk0l17A8EhDoiYAlq4zfX8PJxDD2xZLfGhRn2HNxat7rD27Q_uAlNk-dIDSw0Q"}], "types": ["park", "point_of_interest", "establishment"], "reference": "CmRSAAAAhP6I6mPKxkf4FseideAReHMTLQ3kZe5Ryo9vSb1jOyuhH79mE0A8fY8SHPoflKyRksl5xNt2IVqZ0kkK0SGTa9e2QSS5OqATYnaA80vMXWFEdHXWCX4Ze1wW54nXjbfMEhDc671tRfSBDBhnrjOiRr_jGhQclsbPNJ6iZA79m7swK1hpCEzOnQ", "name": "Houston Audubon Society", "rating": 5, "id": "050a5458d86bdd1cee7b09678bd6256d0a20a73e", "job_title": "Severn-Trent-Services", "place_id": "ChIJlQOxwVDbQIYR2uX_TZl0TYc", "address": "440 Wilchester Blvd, Houston, TX 77079, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.56820189999999, 29.770778], "type": "Point"}, "properties": {"photos": [{"width": 1800, "height": 1200, "html_attributions": ["<a href=\"https://maps.google.com/maps/contrib/108765250995932379967/photos\">Audubon Docent Guild</a>"], "photo_reference": "CoQBdwAAAP0jrSpC7vo4zMTy5mujnBcFjF4wp3j73fqx0dZK7bss7J69CjTjctNZ66VWl2vpFFMOxsMZVguWsFu6K7eM0BOJOlDW28lJ08-DOrmBhRMBj_0q_KoiHP1Lp2vcPK5x5LaajDYiWOv7Bf1qQzJAYsLbhnyI00FrvMPxedNxRVg6EhCHSQ5cEJXLu1BxGIc8TeGFGhRvvTT-3gvo4rYJthQT5dVR03dvLw"}], "types": ["park", "point_of_interest", "establishment"], "reference": "CmRSAAAA5SJ9xN4u87JyyXU-J-ZkQKGMGk-lIIQECUnWS8-pFbIwnt09OtYcxjpRHuXujTDRc2BkwF85BIzXcT_pupUgBSQYeWblK_5ds8wzgWZilE9EEDdk6038d079f985Ej73EhCe2wayqEzzRAAOSh-bWDEiGhSFvnNKeRrC8mT2dh8Ze_Ser2iQHg", "name": "Audubon Docent Guild", "rating": 5, "id": "7ddd5daf76cc4979e2ba6b062322d1c77d5d1c07", "job_title": "Severn-Trent-Services", "place_id": "ChIJI9XyNFHbQIYRtwHb8EtTpeU", "address": "440 Wilchester Blvd, Houston, TX 77079, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.44932349999999, 29.7803218], "type": "Point"}, "properties": {"photos": [], "types": ["point_of_interest", "establishment"], "reference": "CmRSAAAASuTHnpTU-SS1S85pdlvcgz-2-jI_mVZ4j0Kh-1P51bdCEaBarZKBRUYQH7YfyvWc7mshGz7k_cWmeAxg0vfOBIdp6_ZnK4J3YEsDnCN_n-aXjUL_8HBTsjUy4Fdr7nzsEhBXrSObF7RaipSlpfKlBjW0GhQutdyDViDcs5MYTlcxGoewECkfFQ", "name": "Coastal Conservation Association-Tx", "rating": 3, "id": "7258b034e119f31e82320bca6e72781ee9f79d75", "job_title": "Hiatus-Spa-Retreat", "place_id": "ChIJcekacM_GQIYRPzL13cgQrPk", "address": "6919 Portwest Dr #100, Houston, TX 77024, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.47039, 29.655454], "type": "Point"}, "properties": {"photos": [{"width": 5312, "height": 2988, "html_attributions": ["<a href=\"https://maps.google.com/maps/contrib/101184977609161362375/photos\">aug4</a>"], "photo_reference": "CoQBdwAAAOFsQljMsh_4IjDf4slW9BKhobJwAPcIXI45q90JCYbGJSgVM_IcbObl_MDc2t-FE_hcoU1Si3Tb5CYplQR7foGIAb0-oz8L3Y2GIpqKzqsYYpNFbwwEwnaTEMk7P_SrRryOvSpRCOx00vom-u_E058BRp0ZeLBIsL_OZ2e85vT0EhCfpFi7e7laiJEAuaHoXVJ6GhSTKolkrfKA9G_oyjNGLVdauNY_sQ"}], "types": ["park", "point_of_interest", "establishment"], "reference": "CmRRAAAA0Kmhq2zhb8Uuqq3fvLgq7jBYwHd53JFvWZPiw92OSXWknArcvSYFNMXSZKmqO13JVoMh4iKEAn1f8Xl8gDdDd8NNEgYSRPO70Yj4DdC2GGM0nHkTLWcjBTyG2cY6bi9TEhAEMMNTf7QzC23ZzBv5NIuJGhQbvlyIUpqEAU4sjS-W-wPzcfMGkA", "name": "Willow Waterhole Greenspace", "rating": 4.3, "id": "0127506e8071350c2d48f0ca56e939045297a0f4", "job_title": "Hiatus-Spa-Retreat", "place_id": "ChIJR6_2zTzqQIYRsA7wExgfDWs", "address": "S Willow Dr, Houston, TX 77035, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.4003322, 29.7388505], "type": "Point"}, "properties": {"photos": [{"width": 1136, "height": 640, "html_attributions": ["<a href=\"https://maps.google.com/maps/contrib/117056878997299689379/photos\">Marisol Brown</a>"], "photo_reference": "CoQBdwAAAHUCXFSMYFIUyMYLojGNBImZlas_v7Q2Qj740jS9_LZ8czEk9FVlReuP7-sxVWQkoAN6qotTFJvyjY5w37kccVf3aa57jkWNcarcSmHLJdzJbgNGSXvvbdaWkzutTSCuBUdaRsfwXwp6tZFU1XB7WQu6LDDKGk4BACqVAABqrlXYEhAI6_kyE8COkzC2VMtmA_H7GhSJRI7_juHAHESeRtfd1QdTZtYiVw"}], "types": ["point_of_interest", "establishment"], "reference": "CmRRAAAAU7kfGStoAiXMCVG0pPj41VT6r2uDId9T067S0A8BFYAlV2XB4950UBJWW1apLiyWuHm4WqPKjfXdqFRV9O51HbeQCOKwh_LbW3zFUaupjmEHiy8CjAYvybv5-nm8_fG1EhAt3kZGmXItecuWj2l8XU16GhRY81YJ8Ko05hMSDk1WU9WcFXW7lg", "name": "Masters Fine Art Conservation", "rating": 5, "id": "a462c2eef4e22ea319485ae7b84f3d20756cbdd1", "job_title": "Hiatus-Spa-Retreat", "place_id": "ChIJp8u2bZvAQIYRbosnWz6cVmY", "address": "1612 W Alabama St, Houston, TX 77006, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.3876169, 29.794149], "type": "Point"}, "properties": {"photos": [], "types": ["art_gallery", "point_of_interest", "establishment"], "reference": "CmRRAAAAoFWFtzPr08bJQ1MGgyAUKfCRdcblNUdvy9bdgxMpADJgTvPsv2uplYh6TL2iHe6dnxeoLKnqzf-A8HrNRMVIOax1e8o2VerV1wOaZMNE50GlaTnU1VCNkJ36SFXez6EmEhBccAIv1rI8uAWG3kIW6rBoGhR4JAoEs1ofC8XPb5u66XigLV5eEA", "name": "Whitten & Proctor Fine Art Conservation", "rating": "NA", "id": "883a8c5ef35ab28e1630235ad65a6b16506a67fa", "job_title": "Hiatus-Spa-Retreat", "place_id": "ChIJ8YuXE6K4QIYRn1SF1hazFEw", "address": "1236 Studewood St, Houston, TX 77008, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.3858767, 29.7300997], "type": "Point"}, "properties": {"photos": [], "types": ["point_of_interest", "establishment"], "reference": "CmRSAAAAIRQVFoXiANAEDV_oQUaCSKdIdaoUn2QBRFqBY2GvHPH-fnBJ54nAwtcCt_PYWyLZ3ip_G5mp-5zt-jb79Vlo0_ESlmb8_ORAefVoR8NIk5oKyvccKxkc4JPxa9wVkQbpEhCeHuJ2Eho2WpAXHrkFsHTFGhTiZRiUK_8qI4ERqYhgP5EbouZYog", "name": "St Mark Fine Arts Conservation", "rating": 5, "id": "ea2d4bac6d74716b33f456dff3aae0cc0b43cca3", "job_title": "Hiatus-Spa-Retreat", "place_id": "ChIJKbDEoXm_QIYRcRFBlp0dE8A", "address": "4901 Main St, Houston, TX 77002, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.483218, 29.7482286], "type": "Point"}, "properties": {"photos": [], "types": ["point_of_interest", "establishment"], "reference": "CmRRAAAAYqdFYiy170ATxqJVJPClHdJG8zDjKJXpfgJpyOngKs2RVlABnuN_sGFZ-ZElC7IniLQ_9Br7uNX_zwzWIOQGfcYClqclFrfn7uN8Io9ZSpBRi8SEBnKDPVZYB_XkmZyyEhB2VN4tLtEv-WiKcD1_1iRQGhRWklallCG7zwA0qWmoPbkVAegQNg", "name": "The Nature Conservancy", "rating": "NA", "id": "90af6fb9fb926dde9f7103577cebc4150bbb1dec", "job_title": "Hiatus-Spa-Retreat", "place_id": "ChIJq-m4EX3AQIYRJkn4Lhccp2E", "address": "1800 Augusta Dr #240, Houston, TX 77057, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.42318089999999, 29.7345943], "type": "Point"}, "properties": {"photos": [{"width": 750, "height": 437, "html_attributions": ["<a href=\"https://maps.google.com/maps/contrib/106788706324997826205/photos\">Erika</a>"], "photo_reference": "CoQBdwAAAF0v1tmjn55TawSOD5YhW-Vly9zrQZijOuMIrCjU6py_Gs5VvhfHuQ-OBQl8UNX27VrpnsxNjGb_EzsgoxBm6AdAjfK24dYSSAdJpUNwM2l8EISqe87BUb58zQVV7yHXK3ZKvAl9NGt-ZPDKt_fnmoLu1YfMJUsKK-5fF7OYwvkpEhCz0gtgvwihtLkmsVaApp1-GhRFvdS6EtGA80j82_sVOZ4ZBr-6dA"}], "types": ["point_of_interest", "establishment"], "reference": "CmRRAAAAZJSGeD25Pn4gwP4DU9gjOrQFLLoPYSc4FUwYeN33HORLxGjx7Mfb_ygkcHfc0D1-2diUC4doKhhqXSfz10PVvjRdW1SNWgXHdUkP94eXd-SECjHRrZJZCAmWRqC6yn1pEhCnAMydxxkweTPqhvFDGP7NGhTc_qgm7BVhECICObI4sKJ_Oeqdgw", "name": "Student Conservation Association", "rating": "NA", "id": "1c5ea7722fc0d99e9f7dfca55f5d9078224d51d3", "job_title": "Hiatus-Spa-Retreat", "place_id": "ChIJQcqBXfDAQIYRErawO-goGj4", "address": "2990 Richmond Ave Suite #400, Houston, TX 77098, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-96.038102, 30.055621], "type": "Point"}, "properties": {"photos": [{"width": 984, "height": 985, "html_attributions": ["<a href=\"https://maps.google.com/maps/contrib/110279808588468038448/photos\">Peckerwood Garden Conservation Foundation</a>"], "photo_reference": "CoQBdwAAAMFn9gKiRL7VmUGN-jLH7LreBy-YUbscFi6XG2D-PbmgvVt6cJcGHgxOVkQDrqp13lnJkoJ4wCFqckBaKtzd_2H118uoPdGGDvxvYNmEuZUthR7v3cqYla0aDWLyomditz1VYB7tq4OIHmfaa3Eu4xGw8L7DJ0h9fsp1_B1SrBXtEhC5W7AFExTKgDQvzRaL2MnsGhTH84ZfPpAPoowvp-pQhHreuqosPA"}], "types": ["park", "point_of_interest", "establishment"], "reference": "CmRRAAAAaPYVYn-nQitFn7kEAanYmxcumB8FkjY3w07vuJ-EXbZVZml18K-n3tkKa8jvf-TQEFgdhnBqRF82Yd9h1a6tGvsdSiF9ZnfqlxF7x716YJAZE7HTYJ-eM-gDoyOBx5zqEhDyXX6CVfaDuKbPtyZFYrDwGhQV2kW4wPo8HhFKcFOQ4tavNndzGQ", "name": "Peckerwood Garden Conservation Foundation", "rating": "NA", "id": "e618a4c618cd67ce4f5fdc165f640220ab3b53b2", "job_title": "Hiatus-Spa-Retreat", "place_id": "ChIJmUR7pvHKRoYRIIl0o73bPGE", "address": "20559 Fm 359 Rd, Pine Island, TX 77445, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.64386449999999, 29.7515036], "type": "Point"}, "properties": {"photos": [], "types": ["point_of_interest", "establishment"], "reference": "CmRRAAAAkbEeatwILFgkeYOdL6iqUwkOVvk9whSkxkZpJyLL39pw9ZLrv4dsOkzyVBrsJHCaPSURJXV46_7vUl-obM--V8qrYWa1o_qvqmnFhNwbvw2XY-IlGhe9QsvrOeAuxSLtEhDQAwprIu2NUwgl-1DB9U0QGhSyEg2DZF9mqJgRWi8zersS8J7how", "name": "H2O Conservation Technology", "rating": "NA", "id": "30c07988ef8dfc62dac712b9d587daa4a36f2539", "job_title": "Hiatus-Spa-Retreat", "place_id": "ChIJIWZRKeHKQIYRXxta3wOMGGc", "address": "1725 Hwy 6, Houston, TX 77077, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.5705632, 29.7714443], "type": "Point"}, "properties": {"photos": [{"width": 3024, "height": 4032, "html_attributions": ["<a href=\"https://maps.google.com/maps/contrib/108143329814504597326/photos\">State from Jake farm</a>"], "photo_reference": "CoQBdwAAAJVA04ccnju_FLMCbaM4v-8dLTp593Vl3cenM7FcdAwB4ynQRiVpcvceookuLhPaMj87Q2JtMZR7CzFRyjqoVHin3nKCUKxjRrgqupa--uQTiteF1Qr4MDShfql6Zdk6afDrj6tj6fpG1TibQ75ON4NNr3EY5QY2v6H1C8057LAVEhAfJFksfMnx4mSfn5out9gFGhRrWh6hqBy4ZcZwr2--glh4kf2_xQ"}], "types": ["park", "point_of_interest", "establishment"], "reference": "CmRSAAAAGKdKqUj54rn6dZdt1JOCpwj-evUlFUww-HkGcElmYk-pBiTzx0Yh2K30gY38i2k3wlCy2PqYbGuGuY0IUZKar-k2aTrvVGKXGAlJhPVg_rAzQ9v6cqwAlWQi89yaGusPEhBcXJef_xX6-wphg1is6nrxGhQ1KbVXDWrdE9oeKAqdfZ8DMt-Omw", "name": "Houston Audubon Society", "rating": 5, "id": "050a5458d86bdd1cee7b09678bd6256d0a20a73e", "job_title": "Hiatus-Spa-Retreat", "place_id": "ChIJlQOxwVDbQIYR2uX_TZl0TYc", "address": "440 Wilchester Blvd, Houston, TX 77079, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.56820189999999, 29.770778], "type": "Point"}, "properties": {"photos": [{"width": 1800, "height": 1200, "html_attributions": ["<a href=\"https://maps.google.com/maps/contrib/108765250995932379967/photos\">Audubon Docent Guild</a>"], "photo_reference": "CoQBdwAAAAlDGsNOKEcjXNTbxNBT9Mh52eIYuLXRX7Wku7Lb0veQHOpZmm2sQQPjy-Oi--j62FP_BB2kPMAqGiIJwOfqvtKQXRgDmIMgAg1xsHuxsrWSFo3IxiDpf_GuTlL72HALH1IEg0CulTCuJGZnSYLe3Zc3aApVEUZUxOWoWbPJSEY6EhD0nRqcSsbKCK7KKwtr0_7rGhScYVraODgTGkj37f7as7zAAsmm7w"}], "types": ["park", "point_of_interest", "establishment"], "reference": "CmRSAAAAkQit0_TO7E7tkoK1uC3FYPuvQyh5VFzXpcLLbs1lsLTEKL9MxIGtu87VHMd4bc-s5sayBTeZMA9xor3O_QYIAW_5N6kF8BJ6y3rzgTnW2UyNgPaizEh3K7LLu6RHg-EiEhBA8Iiy4oeanrJ9so8AdfdzGhSqxRDpwTF2cPM_mlkxGw0daNvmTQ", "name": "Audubon Docent Guild", "rating": 5, "id": "7ddd5daf76cc4979e2ba6b062322d1c77d5d1c07", "job_title": "Hiatus-Spa-Retreat", "place_id": "ChIJI9XyNFHbQIYRtwHb8EtTpeU", "address": "440 Wilchester Blvd, Houston, TX 77079, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.44932349999999, 29.7803218], "type": "Point"}, "properties": {"photos": [], "types": ["point_of_interest", "establishment"], "reference": "CmRSAAAA84wkuQohxd6qFeFa_-UGjafFebfNlSka77AJnkOHaQ3EuEzbMjXL9hPu_XfD2kpVlklO3XV8wLEaVtqpGAHt0pPXEPYmFrsIq6NDBu8Um4pqAkALGHYClbXPqteKHw9NEhBLVhlGtXWG9X_rk3gh1p3KGhSu9lprLpFrnlmFLYLNvU2IKrGq2Q", "name": "Coastal Conservation Association-Tx", "rating": 3, "id": "7258b034e119f31e82320bca6e72781ee9f79d75", "job_title": "Kaplan", "place_id": "ChIJcekacM_GQIYRPzL13cgQrPk", "address": "6919 Portwest Dr #100, Houston, TX 77024, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.47039, 29.655454], "type": "Point"}, "properties": {"photos": [{"width": 5312, "height": 2988, "html_attributions": ["<a href=\"https://maps.google.com/maps/contrib/101184977609161362375/photos\">aug4</a>"], "photo_reference": "CoQBdwAAACg0fmvXNKbzfjFVQycvtQTORP-vXQaNhTUxNr48xKkgeDSJW-m-dXv9cDqGcwZTQbX1LIG5RJC7LCGAtliZTCkvAnIr2bQqnBQtr9GSlkYTePFAoTcxy6tUbZxppPOcNUY2XRuCF7CwnhP87whLlHqrOvWufI-toKyX3E5_qYWvEhDZhZV7fG52H9EzFzX0GUwDGhR0T--UK-4cuk5ihrugKhpCbDH-9A"}], "types": ["park", "point_of_interest", "establishment"], "reference": "CmRRAAAARlXh6qDRg8tpM-U_Bs6VXWZ1D-ZZuvXcKaNXMFc58MsdcoxaOpmpah7pmW3bAB2k35oU0__E400ErBKS6JlPQhOGIizzb1OWGeHGHQYlx_d0Wk2tMIzRsSMgwOwV0GRZEhDkyFSY3FMWftsx1S50xu1DGhRCuHkXsRG7oYBhltgyERz5OWs5wQ", "name": "Willow Waterhole Greenspace", "rating": 4.3, "id": "0127506e8071350c2d48f0ca56e939045297a0f4", "job_title": "Kaplan", "place_id": "ChIJR6_2zTzqQIYRsA7wExgfDWs", "address": "S Willow Dr, Houston, TX 77035, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.4003322, 29.7388505], "type": "Point"}, "properties": {"photos": [{"width": 1136, "height": 640, "html_attributions": ["<a href=\"https://maps.google.com/maps/contrib/117056878997299689379/photos\">Marisol Brown</a>"], "photo_reference": "CoQBdwAAACoMd7gogkA5PLLKf6gBsvT8GxmtwcCyOTH99hkSIm89ujHIscJACOWW1VRnaTrlBe_XvYKNVHsqhuHZ6xiFr2tbIzoBQxe7ZB8D2lXzag7YLrxbKgjVZnGGHxK5GeJC6lRjIEjnBWX_JoGsTUXFNmehC3mbd-S2GR4nOoBpPDw-EhBI-BftdaV8aaVTsF5byXYtGhQ6CRH1RLqSsC1-rdvcy1uNuWU75g"}], "types": ["point_of_interest", "establishment"], "reference": "CmRRAAAAwyE-uUGK_XHclznfIV1PpGpLsrHxTxLDdHrXNe9GXaubxeE7MDkkrKTJcHW8guf2w5z4b9SF_rGgrnZZjtmYfBthUnTEJ9TkoE1N0Ori6dfUtD409HyruB8vxBq0IkywEhCqAuRauHfczW-F9zEBAE9IGhTsaOO33LaPx2R_lxjVu5vNO35bFw", "name": "Masters Fine Art Conservation", "rating": 5, "id": "a462c2eef4e22ea319485ae7b84f3d20756cbdd1", "job_title": "Kaplan", "place_id": "ChIJp8u2bZvAQIYRbosnWz6cVmY", "address": "1612 W Alabama St, Houston, TX 77006, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.3876169, 29.794149], "type": "Point"}, "properties": {"photos": [], "types": ["art_gallery", "point_of_interest", "establishment"], "reference": "CmRRAAAAecFkZcjesGqIvZaUbbMQWJiwhGw9oJpAs7CFrbuTciQ8BCN2o0OZsFd7Rbv_6pSclm64l0SorMPNfwopGUcnq8mQo5ppOiebXaNCoAE58444lgpuLdpPftSWw7Ag7QiYEhBxf1b0GfFSTIvUo5UpGbmPGhS7VX1ssrlrHoVnN1vTEPhj8TiXog", "name": "Whitten & Proctor Fine Art Conservation", "rating": "NA", "id": "883a8c5ef35ab28e1630235ad65a6b16506a67fa", "job_title": "Kaplan", "place_id": "ChIJ8YuXE6K4QIYRn1SF1hazFEw", "address": "1236 Studewood St, Houston, TX 77008, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.3858767, 29.7300997], "type": "Point"}, "properties": {"photos": [], "types": ["point_of_interest", "establishment"], "reference": "CmRSAAAAHNcdXSuiMm5V8Gt1dDr92NWM2NSzUkxwCH5IxlGazd0CVNyeORXNkuA_rcCZWI2NPurYQtXVdG1Y1qtUztF5iF1OidQBrhE5DQARi67bPYWorRdXabtr8sb9YYPQ3W_gEhBho5JBsajzaLv6_gUV9X6HGhQdQdBdHrzibLJ_T-SwmBykw_1-sQ", "name": "St Mark Fine Arts Conservation", "rating": 5, "id": "ea2d4bac6d74716b33f456dff3aae0cc0b43cca3", "job_title": "Kaplan", "place_id": "ChIJKbDEoXm_QIYRcRFBlp0dE8A", "address": "4901 Main St, Houston, TX 77002, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.483218, 29.7482286], "type": "Point"}, "properties": {"photos": [], "types": ["point_of_interest", "establishment"], "reference": "CmRRAAAAgrjQklDDhNY4Syq-ypl0APa9-cUERPemSEDlAPxA7D4L-tHyCbemAhQExuFjrDsAUPuRM5W8VH3fkB3NCT4VIRvuVZzEy_7kk0b6aBrgN4vYhbRLsUIXaWGyfy6dB2GYEhDvRWeBZESisaEJmnf_fJGVGhQJlBbSYqOhe-JK6p4wY-2Z3GNjzw", "name": "The Nature Conservancy", "rating": "NA", "id": "90af6fb9fb926dde9f7103577cebc4150bbb1dec", "job_title": "Kaplan", "place_id": "ChIJq-m4EX3AQIYRJkn4Lhccp2E", "address": "1800 Augusta Dr #240, Houston, TX 77057, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.42318089999999, 29.7345943], "type": "Point"}, "properties": {"photos": [{"width": 750, "height": 437, "html_attributions": ["<a href=\"https://maps.google.com/maps/contrib/106788706324997826205/photos\">Erika</a>"], "photo_reference": "CoQBdwAAAF_0HaTuZo1DQXuxkw86etQe8gQ_Pac0bfvgE8v-5vlWZPsCdQf2TMyarZ2b_vs3Gqa2ppSkyyfTSh6xIKJAttyFWnk1WeiMK6WG3dNRZlIg-i5S-FC7JrlILc4cf63ohN1hPu-PgII2vVUpq1oFSFccuA6NMf7gierOd_FEaWV7EhAKMqdezzJ4NPo17pQQ-JfoGhQ8ilfTJhWkWyydDAKD4Ec1G-8hyw"}], "types": ["point_of_interest", "establishment"], "reference": "CmRRAAAAmFf1JjvYcl1Eer3ZUAyuG9Kcxo4PcGNx1PkXCfOAnzGyQzWllQtDO07xJEdX6WNfkbKxMiQNeQjuVn-Hho5L7wtpbizoYC_KIZaybMj52hgUsLvfP0k8vMOno_qQPA_CEhAqyH48Ml1bGZ0pWMHlX0ezGhS6Y3CCu1NQfqxkH1MliP6JiKjMgw", "name": "Student Conservation Association", "rating": "NA", "id": "1c5ea7722fc0d99e9f7dfca55f5d9078224d51d3", "job_title": "Kaplan", "place_id": "ChIJQcqBXfDAQIYRErawO-goGj4", "address": "2990 Richmond Ave Suite #400, Houston, TX 77098, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-96.038102, 30.055621], "type": "Point"}, "properties": {"photos": [{"width": 984, "height": 985, "html_attributions": ["<a href=\"https://maps.google.com/maps/contrib/110279808588468038448/photos\">Peckerwood Garden Conservation Foundation</a>"], "photo_reference": "CoQBdwAAAHhOS37cKyMCmeOdCqxJFT2sCD2JxJZb0atqWVdTljQEOAsNzNtoaBD2Pe7tpbAeugqqY5b2C-aN8y5ON3AodKxkLpDYp8eUCB-flyqhfM06UCpqxX-7U0HbEOW1rgUaaeftG8JRrNjqNB2iNnnRIyFNFaPzcPnnBmQbdXS6I-0UEhBmCZQgk6LwkWFiqW6BWg1MGhSdOzpFCXOHmJrNsA16y37rMz3bRw"}], "types": ["park", "point_of_interest", "establishment"], "reference": "CmRRAAAAFWaS616Fii4s-3ku7PwEWkkR0Hb7F4NPJz8tzBbRZwKyly8vUf7GTLj0BXfHyACf0SpnuZjkLteZsAo9442LO_VFKcE94DQEV5-3wGDv8qGdl704I2SOtaSENH9eFo29EhBkOL9jFeaF1RmEJhbjNegdGhT4eyxldx0uSi1agYzKxW8Fr3lsmw", "name": "Peckerwood Garden Conservation Foundation", "rating": "NA", "id": "e618a4c618cd67ce4f5fdc165f640220ab3b53b2", "job_title": "Kaplan", "place_id": "ChIJmUR7pvHKRoYRIIl0o73bPGE", "address": "20559 Fm 359 Rd, Pine Island, TX 77445, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.64386449999999, 29.7515036], "type": "Point"}, "properties": {"photos": [], "types": ["point_of_interest", "establishment"], "reference": "CmRRAAAAiex4TeZSbIf6J78Z_2xgDlEghJy4CHiQ-_E7HTpYggDx4_CmwtN9Ox5SwWGi9_-BIxrXPFJGnyK9IKU-zDuceL5LpkgWc8Z1EWodXY05Y9M1uMFeMJOeYJ8vYTqCqoBSEhBfPs67l8V69_aKbU-h-LKQGhRfn9cqSbu8Gj9tLVsO2NPEKqPBog", "name": "H2O Conservation Technology", "rating": "NA", "id": "30c07988ef8dfc62dac712b9d587daa4a36f2539", "job_title": "Kaplan", "place_id": "ChIJIWZRKeHKQIYRXxta3wOMGGc", "address": "1725 Hwy 6, Houston, TX 77077, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.5705632, 29.7714443], "type": "Point"}, "properties": {"photos": [{"width": 3024, "height": 4032, "html_attributions": ["<a href=\"https://maps.google.com/maps/contrib/108143329814504597326/photos\">State from Jake farm</a>"], "photo_reference": "CoQBdwAAAGF8RPdPA7KQy0Zj6CEviXerA4ubeQOBK3CyVL8p68hUajmb1tg8ZE3B-IaJkSQ5Ltwp6qD5AIxmjspOYeFqfMCBNkx27vSYhZ4vkhdr1I7t98gLTGEDAyUJEYByzrejdEwR7pxau8fSRjyBwjhoxotgqjulJ2Hyfazqf-s7__W7EhDI35GfQug-dapnO2CxVg4BGhTqX6IUdKv_FOpktGWQ91XZDqjuKw"}], "types": ["park", "point_of_interest", "establishment"], "reference": "CmRSAAAAOOgK_8SAmsrzyEGqh8QqIg9l0naf86w9XEdymBna6cYysRy-w22cEkPgPPb3yISFGTXQjLO8aYU8NyNkitXeOD7CophdOctkgKI9YhMFNHHkj-YsXrj5mokaZ8NQa8gjEhCCUk_GhHTTalkNBoOQywApGhTpvE41VLAdTslUokMDOsDfU-WcLg", "name": "Houston Audubon Society", "rating": 5, "id": "050a5458d86bdd1cee7b09678bd6256d0a20a73e", "job_title": "Kaplan", "place_id": "ChIJlQOxwVDbQIYR2uX_TZl0TYc", "address": "440 Wilchester Blvd, Houston, TX 77079, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.56820189999999, 29.770778], "type": "Point"}, "properties": {"photos": [{"width": 1800, "height": 1200, "html_attributions": ["<a href=\"https://maps.google.com/maps/contrib/108765250995932379967/photos\">Audubon Docent Guild</a>"], "photo_reference": "CoQBdwAAAIcIbr7phLyU0SQKyt5XwnbYV0cpVm70zbIwHFksgN8nAd8_2zu4C1SiwN9511HvazsP_gBU9gBVolOn_K8lDO9Zg5xCa1Oc2v8aem7nqx3f85rWQaMcLKySURuZ_xw5k8EsJfCia09Kq6ChYbpCKHir0WI7f_scVllQqhG8IMujEhAsmsU_l9jrxmATs7bcVf58GhRPI-QehC6ASysGSSieLnxHWU-onw"}], "types": ["park", "point_of_interest", "establishment"], "reference": "CmRSAAAAMn3okTv806_i59pOOZrB4EszWpm4-cPoZP-TcORXUun6p1Q7wrrREeVteieqAHYrveasBQbsRJNE0rMlspQq9VwGE5e5SPqgtoAC1E7CjTPnG9bSEpn6RpHSW_NIo9fEEhAvPyqVKJXJPVju7WW6YAr1GhSfyXgwQzFYhHhyYSn4DJe_SzFzMQ", "name": "Audubon Docent Guild", "rating": 5, "id": "7ddd5daf76cc4979e2ba6b062322d1c77d5d1c07", "job_title": "Kaplan", "place_id": "ChIJI9XyNFHbQIYRtwHb8EtTpeU", "address": "440 Wilchester Blvd, Houston, TX 77079, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.44932349999999, 29.7803218], "type": "Point"}, "properties": {"photos": [], "types": ["point_of_interest", "establishment"], "reference": "CmRSAAAABYUK6uuOMn6vZ3Xy9YUWBHegYSz2ZceEYKkbi7Bzn_rfrB32iDfFWi3KvCPia0dMdU3vzxPINuLWJXnHqf1jmVZ4hDWjH1KMbL4gE2ECyRMkTNp5MdR4ISSE9eJdGkDwEhDEfDVun9rHILKNgHUWVcgKGhQtl3hjQcSa6SOxdC8EC4ZvSU15rQ", "name": "Coastal Conservation Association-Tx", "rating": 3, "id": "7258b034e119f31e82320bca6e72781ee9f79d75", "job_title": "Best-Buy", "place_id": "ChIJcekacM_GQIYRPzL13cgQrPk", "address": "6919 Portwest Dr #100, Houston, TX 77024, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.47039, 29.655454], "type": "Point"}, "properties": {"photos": [{"width": 5312, "height": 2988, "html_attributions": ["<a href=\"https://maps.google.com/maps/contrib/101184977609161362375/photos\">aug4</a>"], "photo_reference": "CoQBdwAAAFFuRDLIuAhAEwNm7_BSJGAHKnNMlmONPLbozohsMzJgNENBDejvHqKiTjbQcVcCa-A6ktOnDq8KIyI1GTGtjOypInGG5P5bzooEq8YfFK6OF4g_GlJT4gPm8396nlJnNi4yK469mQbFsaTo1fHQX21ri-PyFq8w8VkUwKp41L-mEhAeIKwd-HYhN4g3UR2GmzBDGhQXVaxVyM7DMxwoVoZbZCE8uob19Q"}], "types": ["park", "point_of_interest", "establishment"], "reference": "CmRRAAAAJp56cMEcUqVRotzaEu6xQa7FkrO7YRBRz-NUqq29S4JVOwyMI9OP9eN1PwqztF49CjabP347Tk4v18DfCqtVaAPxspNrqCbGoT1xSsVhPOvbyDjR9cUP3N6HGDamKGyNEhCFn7kUhUfNoijzdGlTeUbCGhS7Hg2ZPoBOy7yAIak4rv1Ilo_iRA", "name": "Willow Waterhole Greenspace", "rating": 4.3, "id": "0127506e8071350c2d48f0ca56e939045297a0f4", "job_title": "Best-Buy", "place_id": "ChIJR6_2zTzqQIYRsA7wExgfDWs", "address": "S Willow Dr, Houston, TX 77035, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.4003322, 29.7388505], "type": "Point"}, "properties": {"photos": [{"width": 1136, "height": 640, "html_attributions": ["<a href=\"https://maps.google.com/maps/contrib/117056878997299689379/photos\">Marisol Brown</a>"], "photo_reference": "CoQBdwAAAE1FFBK_K3R7BQQOA6o3BYOc2ig1TEB0MX2hmxnr1CG5FCS6g2IB4hfwACIi2MJxI1ax2BzY_RigSuPui_EB6ODzFqIx5WFS44eWxjDVpAhrtT4YKaQYjbCmbITU9D1ZKwJrDesaCYO1JBoTAW2Qxz0O-GCMByX0lXZynHTs-wjPEhCGpSuqVcvrKo_QMwlfq1r5GhTYW4F3AMaTTAh35EJj-ECiE9_bCw"}], "types": ["point_of_interest", "establishment"], "reference": "CmRRAAAA03wG0XXXpHFosEMHFBSYdhTwrqZHmIO8qSXEjZdG5mFBYl4gSUjdxRkWjwfwP3UvcuWvUWexI_R6r6gog17OUAsLZd3lPrAfA3DsSGiezO8MKP5QuM2T23BMIJiBri5UEhCgBWhy_23OjDxSL2yEm6OMGhQ24x5D-2e58Q__3UGrIW1hphlMUQ", "name": "Masters Fine Art Conservation", "rating": 5, "id": "a462c2eef4e22ea319485ae7b84f3d20756cbdd1", "job_title": "Best-Buy", "place_id": "ChIJp8u2bZvAQIYRbosnWz6cVmY", "address": "1612 W Alabama St, Houston, TX 77006, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.3876169, 29.794149], "type": "Point"}, "properties": {"photos": [], "types": ["art_gallery", "point_of_interest", "establishment"], "reference": "CmRRAAAA0Rd0eHbsNMeuzYrZZIqA1MCzJbFNW6teKEqFR8V7XDBn_FqRblV0-1hn1QqgRFducyUvsQ-0arZmNO6bw8zfsvlRAPHSflOvsGYCXvfOM_ndAGJ_2mj8rkEamNiDo2dZEhAhzaGrde5tnBpYah5mqHKiGhRhCGgP1iuL7ry85mxZvT5VAEqegQ", "name": "Whitten & Proctor Fine Art Conservation", "rating": "NA", "id": "883a8c5ef35ab28e1630235ad65a6b16506a67fa", "job_title": "Best-Buy", "place_id": "ChIJ8YuXE6K4QIYRn1SF1hazFEw", "address": "1236 Studewood St, Houston, TX 77008, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.3858767, 29.7300997], "type": "Point"}, "properties": {"photos": [], "types": ["point_of_interest", "establishment"], "reference": "CmRSAAAAohEbhZ_eKizGWNpbhTOM-NO_Jzw5Yc4Z8V9cmlnZo-gJxfY0tZqaJrdx7geFZwKESk4ryTPWUh6fIB_2-Xp6-F9N-FAnsyIN_c4lzOr_hM6vevEX9SXm25c96L9pKV-rEhDwOsD44SiNmHp0cTOUJJPAGhQfqaPIZY2mkdDKiLDLIZlfJpiTBg", "name": "St Mark Fine Arts Conservation", "rating": 5, "id": "ea2d4bac6d74716b33f456dff3aae0cc0b43cca3", "job_title": "Best-Buy", "place_id": "ChIJKbDEoXm_QIYRcRFBlp0dE8A", "address": "4901 Main St, Houston, TX 77002, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.483218, 29.7482286], "type": "Point"}, "properties": {"photos": [], "types": ["point_of_interest", "establishment"], "reference": "CmRRAAAAYAA3vJcrGxPWOFuMLYtfOMmykW3PcF4lmsWwzBiYP7sxy6xlyqAqb2sSC99jibc7Wjw-00dgyRDaatrRAvOlCsRed1tW79XkQEt6_C2LUXuKiGxD1hTVMr2_6ZVAgPwEEhAlYvnul9xExrD1nplc2P31GhTWNSybYVhwUPXZ5ptyXbEB-d0RCw", "name": "The Nature Conservancy", "rating": "NA", "id": "90af6fb9fb926dde9f7103577cebc4150bbb1dec", "job_title": "Best-Buy", "place_id": "ChIJq-m4EX3AQIYRJkn4Lhccp2E", "address": "1800 Augusta Dr #240, Houston, TX 77057, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.42318089999999, 29.7345943], "type": "Point"}, "properties": {"photos": [{"width": 750, "height": 437, "html_attributions": ["<a href=\"https://maps.google.com/maps/contrib/106788706324997826205/photos\">Erika</a>"], "photo_reference": "CoQBdwAAAEaktRxgKpQxQ6T6polwssS8V0pk-KeiNWAlR1_3bl2b_AuoteysIE0nr7gqkm7ClAG26jERCi81lULKeUJJtfc2uDh-2EjvC9cLXiQE2N9mYxs3DwMzBAaWsQqpor-rC-Tsu5yU_FwzMwZWu5Q63Yjbx1O2Ir6P_Ir5rvhl4sZpEhDot5B0so0g8Xfy1IYmVW4RGhQ2RA7UK910OIq56a1U1bzTn9ffuA"}], "types": ["point_of_interest", "establishment"], "reference": "CmRRAAAA0G-9wSApNrkv0VQKFJc-TkgmcMuCJTH_zuwQJUa7v-EMmqvWmAG1aMPz9ueg9jp8ytNtut7y2DyugQhSwGxGWMxFuFGuKKRqxl_9BGs5bmq3myCf9aD7kZuJwMgkeVzrEhALXWCEHEcveU76TOzfYn0uGhR6V6ThM6KMjPFbA3Lx-kRNtiNdtw", "name": "Student Conservation Association", "rating": "NA", "id": "1c5ea7722fc0d99e9f7dfca55f5d9078224d51d3", "job_title": "Best-Buy", "place_id": "ChIJQcqBXfDAQIYRErawO-goGj4", "address": "2990 Richmond Ave Suite #400, Houston, TX 77098, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-96.038102, 30.055621], "type": "Point"}, "properties": {"photos": [{"width": 984, "height": 985, "html_attributions": ["<a href=\"https://maps.google.com/maps/contrib/110279808588468038448/photos\">Peckerwood Garden Conservation Foundation</a>"], "photo_reference": "CoQBdwAAAAtHO8TBz7Rt1Uun9sDtWJz1bDW4URGrc_deEKBvt5MLYli7zmKAQhLT_TViICYkj7pnANR7FREjG1dfViffaAUM6edqrnYEpX39dA_0lBsVoodcKOfaLb8i52nuw47N0dd83qhWFiU2fJ5dT5BZPPIQGuYKWmWYrHiF0i5HuxEhEhCNQFYcjYE6eWjtftrdKQx9GhSsrS-MoEyZncVswmIg1NoNXAnG1A"}], "types": ["park", "point_of_interest", "establishment"], "reference": "CmRRAAAA_GKUC2cH62Ja_6SnuMaTiel1J6iegodqCicJ_qySJXNYG8_MMqs6wd75kMV8_CeDuqM21YmfkfX2ForBd2AYnNxc5OlaWSiGmxHWAplu2X8MQZQMvdZ8jx1tVoglKQJdEhAX4ZrSXxKs2EtEc6NsfM6bGhQBTMy-XeT8IYXZZFPH6y6OPfio1g", "name": "Peckerwood Garden Conservation Foundation", "rating": "NA", "id": "e618a4c618cd67ce4f5fdc165f640220ab3b53b2", "job_title": "Best-Buy", "place_id": "ChIJmUR7pvHKRoYRIIl0o73bPGE", "address": "20559 Fm 359 Rd, Pine Island, TX 77445, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.64386449999999, 29.7515036], "type": "Point"}, "properties": {"photos": [], "types": ["point_of_interest", "establishment"], "reference": "CmRRAAAAIfT0XnD0onob4726HMB8d4i1uECIfhteGWHvJGTFUx4Dl3xNImazivOzuJmhTA_WY_JL0xMOl1IYypDoZJeJtqFl7E3HhMGBFBIGA1CpTY-Fm7QSxCZavtJhm0aWk3eZEhBgju7zCO0yqlhdzS_B23d7GhR039-s7pN6LGZVnAQBvIQsFu7h0A", "name": "H2O Conservation Technology", "rating": "NA", "id": "30c07988ef8dfc62dac712b9d587daa4a36f2539", "job_title": "Best-Buy", "place_id": "ChIJIWZRKeHKQIYRXxta3wOMGGc", "address": "1725 Hwy 6, Houston, TX 77077, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.5705632, 29.7714443], "type": "Point"}, "properties": {"photos": [{"width": 3024, "height": 4032, "html_attributions": ["<a href=\"https://maps.google.com/maps/contrib/108143329814504597326/photos\">State from Jake farm</a>"], "photo_reference": "CoQBdwAAAJGkL3TIqLX3HieuFivD99RENxgpBcPeA2YFrqM9E_vLl5sbLj93yWxvBJyOqrB_x6vo8PZ53CHeEywH2vKvQLkS9y2UVamMLxx7bqHkyR0eh9JepJhJ6RBVqHs3b81l5qR7JULvmeU0L0i6rezwit2F0SKkVJ4ca63mVBbdl_dsEhCawmALMIE1SE8u5GJ2nh3YGhS_Q7IxQR7TGV03vguRhat_bo92pQ"}], "types": ["park", "point_of_interest", "establishment"], "reference": "CmRSAAAA__bZgRpK9vET5Hxqclaxnvj_xRG2Jepl21kkJoz1hcqDZTsEQMp6wh-GlSD2XgnxFKaKcpnMR2kUie36r_C8ox90BWVDIG_f4s8-riyQnZfRGP8D0Od6IraIQb6LNfHeEhA80y9wpDIJJ485ZuqrEz-cGhR-mZub-KO5jaGn9_y4S04QGKau2g", "name": "Houston Audubon Society", "rating": 5, "id": "050a5458d86bdd1cee7b09678bd6256d0a20a73e", "job_title": "Best-Buy", "place_id": "ChIJlQOxwVDbQIYR2uX_TZl0TYc", "address": "440 Wilchester Blvd, Houston, TX 77079, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.56820189999999, 29.770778], "type": "Point"}, "properties": {"photos": [{"width": 1800, "height": 1200, "html_attributions": ["<a href=\"https://maps.google.com/maps/contrib/108765250995932379967/photos\">Audubon Docent Guild</a>"], "photo_reference": "CoQBdwAAAGO-BFbIC3DGHb-BUvuRsrUVjGKBMEWR8ApLSUWxkL-BKTEIkGZvEaQc84wDOKWf1oJYV-vG-moFXP5HMw1QEdqGueABg3EjFjOPX4hT0bgPjLbBDWg300ZFcLECfF2Q7MqACBUFd_C80OfJX8vFh-8qx9KzO1a_6exHXVU8wBqrEhD7mDjNsPGNsMDFp274MwCGGhRtUVz-fVToBaxcerDtKSQ5cJTwvw"}], "types": ["park", "point_of_interest", "establishment"], "reference": "CmRSAAAAXdbVpS1kmfOYwemm_fHRxAUaZDrUSGzZeKvcJa6gw4t8utnEVkXILXnKswJefRHdnbKp1aGV6l-6o5eVX2IO-oqewHdrFMFnTIJXoilVY0qFfyprOVXy-fMtDpjLS9BMEhCP1vsFF7I-UG5mAYPSprpoGhRAIpu1TUmQzS38wCX6IPjwWiaOzw", "name": "Audubon Docent Guild", "rating": 5, "id": "7ddd5daf76cc4979e2ba6b062322d1c77d5d1c07", "job_title": "Best-Buy", "place_id": "ChIJI9XyNFHbQIYRtwHb8EtTpeU", "address": "440 Wilchester Blvd, Houston, TX 77079, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.44932349999999, 29.7803218], "type": "Point"}, "properties": {"photos": [], "types": ["point_of_interest", "establishment"], "reference": "CmRSAAAAmgkgmyoriZjRkhxRYk4i4_VEYjuEN4kwgQl2KAf84ZAdXCq9XlxGJ1ui1VjmoX4FPRRol0-6v3iU0AEORf9gpXM-DW8N6H5LPsSkoGXlJTjLLMUcWxchQC2I2LvwKzt-EhB8TV3lzQCRP4Tp7gk9f3CsGhTd6Drt0xrEGpvki1rJWVJ-hxy3qA", "name": "Coastal Conservation Association-Tx", "rating": 3, "id": "7258b034e119f31e82320bca6e72781ee9f79d75", "job_title": "Edp-Renewables-North-America", "place_id": "ChIJcekacM_GQIYRPzL13cgQrPk", "address": "6919 Portwest Dr #100, Houston, TX 77024, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.47039, 29.655454], "type": "Point"}, "properties": {"photos": [{"width": 5312, "height": 2988, "html_attributions": ["<a href=\"https://maps.google.com/maps/contrib/101184977609161362375/photos\">aug4</a>"], "photo_reference": "CoQBdwAAAPLa0cbaig6UrBO2j70sRwogbq3tHTsdgvaNQdLExZ0EyG869roGGAk5BhIIsUfolz8YH5HjjZTXILkiYMLIQELfbebEdcyhspBtVPpM7wFLV7afFsif9jGw3OZAwrAqqzxcivVsGXXwLBe6BFq6tUcM7aGzQbslj0orSKuFzg70EhCtjzlHYiB9Q3FLVdEGl7N9GhQyQKqpYwlB02CvauRFuxUvMdY9lw"}], "types": ["park", "point_of_interest", "establishment"], "reference": "CmRRAAAAucxzk6gTQ75tt-Un7rMabRqJSM6J4_suDPaUD7J4YkqwsYbmPEUzyLamGPLZC-70YRLWrp6cP1g4DF8QxxtdD9jf4GeZdHNfnOqNfU6U5hkd7MQSBcNEaBVXvQsdGJxZEhARTD9_h0yP4TFAyttpM-kcGhQEG9yVTUsMg2OZZS0Yi6wOmWAfIg", "name": "Willow Waterhole Greenspace", "rating": 4.3, "id": "0127506e8071350c2d48f0ca56e939045297a0f4", "job_title": "Edp-Renewables-North-America", "place_id": "ChIJR6_2zTzqQIYRsA7wExgfDWs", "address": "S Willow Dr, Houston, TX 77035, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.4003322, 29.7388505], "type": "Point"}, "properties": {"photos": [{"width": 1136, "height": 640, "html_attributions": ["<a href=\"https://maps.google.com/maps/contrib/117056878997299689379/photos\">Marisol Brown</a>"], "photo_reference": "CoQBdwAAAB0oliizsYKFG0vsiTOe7NNosgJ1IFFvY7KoFf0Mmmj2C3KwexeQaN4_CN02wS0B9UaeXzLNncOJUVfYjwWkciujEAocyv-KRYmj9IgRQwEvYZWQ4J1MhX5QARLM8JLpivAUOJLzT1tsM3JJCahzjTU8v0yPHTXN9DhsUebyfbixEhDKPshLsY3jVbO1F3bVbsA9GhRfC9V9SY-g8C-KBHugdI_ErqOIjg"}], "types": ["point_of_interest", "establishment"], "reference": "CmRRAAAAGMwIvUQFy0NpGNxmjtyuzHnkfFhHJw9Awx3jZHWC7YI8jgSNKjbrUkXOFSS2mQgomCtAotAVPq82cTrL1CCIK6wNW9ornbvum4kSwXBs9o2ZVm398HWUBKTaQ0W5WydWEhB-HCE3FP9jsZWvXif2EdFzGhSQbMOhepfNCBLjE0ub_a0LJNWIFg", "name": "Masters Fine Art Conservation", "rating": 5, "id": "a462c2eef4e22ea319485ae7b84f3d20756cbdd1", "job_title": "Edp-Renewables-North-America", "place_id": "ChIJp8u2bZvAQIYRbosnWz6cVmY", "address": "1612 W Alabama St, Houston, TX 77006, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.3876169, 29.794149], "type": "Point"}, "properties": {"photos": [], "types": ["art_gallery", "point_of_interest", "establishment"], "reference": "CmRRAAAAcbfvLP2qhZDPa0JXS2NwZgziBrMUg4CrgQ__3jd73xH8gJjpFUesLz4EwQtNAnstk06xxpfKmRmZ_pjvHCIg6fRfhfJrqZpYxedBRID9rfui0WCAa23VqIBlHFCzWz82EhC5g8KmDH-ODtZ4WPeiyIvcGhT6xhqaEueGDxgQB0kXZgf9HdU5RQ", "name": "Whitten & Proctor Fine Art Conservation", "rating": "NA", "id": "883a8c5ef35ab28e1630235ad65a6b16506a67fa", "job_title": "Edp-Renewables-North-America", "place_id": "ChIJ8YuXE6K4QIYRn1SF1hazFEw", "address": "1236 Studewood St, Houston, TX 77008, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.3858767, 29.7300997], "type": "Point"}, "properties": {"photos": [], "types": ["point_of_interest", "establishment"], "reference": "CmRSAAAAJc39PlEXxNkYdU9bGnwpGzq8N2GHOUsM8BjNsou2M8TCFw-lX4VeGoBl1VPlRdfNtd6CF419YZlr6yIvET6KwuqUWQJQdNnRcGc44H3QsitWpQqW-f82KJ_qw0GAo7pVEhBmKZV2W_-zggFJdjP8hHtGGhTSL4YX657MnJV6HFFBlBol72S9mQ", "name": "St Mark Fine Arts Conservation", "rating": 5, "id": "ea2d4bac6d74716b33f456dff3aae0cc0b43cca3", "job_title": "Edp-Renewables-North-America", "place_id": "ChIJKbDEoXm_QIYRcRFBlp0dE8A", "address": "4901 Main St, Houston, TX 77002, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.483218, 29.7482286], "type": "Point"}, "properties": {"photos": [], "types": ["point_of_interest", "establishment"], "reference": "CmRRAAAA2WQvXu7B7SPPIYXxRWLMYJWonsWIXFvdz308tNCJRhgyZkK1owjFA3xj6lbcvjcEr3kGHGoJRaUF1vfgmNjwXdnXOcN0dZsIT_ytLp-IWfI8R6QL_LNXkGV1-MW0I5T6EhDkRTeWUsoNqIjFw8Xph6txGhSpWV4RJRo59tC4i41SYauRFwDLGQ", "name": "The Nature Conservancy", "rating": "NA", "id": "90af6fb9fb926dde9f7103577cebc4150bbb1dec", "job_title": "Edp-Renewables-North-America", "place_id": "ChIJq-m4EX3AQIYRJkn4Lhccp2E", "address": "1800 Augusta Dr #240, Houston, TX 77057, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.42318089999999, 29.7345943], "type": "Point"}, "properties": {"photos": [{"width": 750, "height": 437, "html_attributions": ["<a href=\"https://maps.google.com/maps/contrib/106788706324997826205/photos\">Erika</a>"], "photo_reference": "CoQBdwAAAHqmiTLNkOi_0a7E-4N0-x6_KG6WRDD32586vN6MnJFA7Y3cPle6b0x8MPYF2P0P4dR80jMrGdL7evk47vAzgd6mtgNtwXgJIvnvZXPiQbyj6L8mE53w_okklEVSUrwmHQME5u2CzcqQptWl4itwUSCrM7wJPITcw15ltUEAtH_8EhDNRddVsPvdzB5voyjpa_NwGhTc_1kiRic49rPeBX_LO5a2-LyOiw"}], "types": ["point_of_interest", "establishment"], "reference": "CmRRAAAA4PmY-CZFrdr2-VdTrUAcCES85XNSmfm54ValN4MSmDpNPQPuPgVhVGUvfoiYAzHe4rh2fn1owFt2eCx9YHyoF7sQ_FZfUJMRIqn2Hq-w7xDQT9J4HIMuHZTWs53trwqEEhCBvXQ60-bzoSl-qFZwwibGGhR9ZZBj-inT66aNZpWUTCG3ThnKOw", "name": "Student Conservation Association", "rating": "NA", "id": "1c5ea7722fc0d99e9f7dfca55f5d9078224d51d3", "job_title": "Edp-Renewables-North-America", "place_id": "ChIJQcqBXfDAQIYRErawO-goGj4", "address": "2990 Richmond Ave Suite #400, Houston, TX 77098, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-96.038102, 30.055621], "type": "Point"}, "properties": {"photos": [{"width": 984, "height": 985, "html_attributions": ["<a href=\"https://maps.google.com/maps/contrib/110279808588468038448/photos\">Peckerwood Garden Conservation Foundation</a>"], "photo_reference": "CoQBdwAAAM4RFkKLaJrk5VAYX8qk7IbwY76gA5BblMXx8_I6nE2qJaoXjDTKCNK62s2-M94i67zLZtjPHKGkV_C1cRgU-A-TakptlFdv7j7wkaFRszEOAMvkQZgFxWc0yVqu_iSfk-CZoKmLVnHTGYpmhj-CMkEmPq7t9YPMusZ8hDkoFNQaEhD8h_IkPW2a17rxAqQRV6UjGhQzzUrG6Xc95vjEqkXIGnEMvb6psQ"}], "types": ["park", "point_of_interest", "establishment"], "reference": "CmRRAAAArHaJ8iMINfiLuVfOKI_zBbee5jjo1Q5j92QegC-le5Q12uroMop_xf_IEjORTIs4I3l5oWzXNi7_xRGdVpSRdp_A428ep_p18b0fhYrBbmmaTpzpmnJYXo9vbTxMQ0HXEhB2beZ6prybaSQYfyBjgz80GhRxF_gae2Um4U9lTAqt2_JrHzgQCA", "name": "Peckerwood Garden Conservation Foundation", "rating": "NA", "id": "e618a4c618cd67ce4f5fdc165f640220ab3b53b2", "job_title": "Edp-Renewables-North-America", "place_id": "ChIJmUR7pvHKRoYRIIl0o73bPGE", "address": "20559 Fm 359 Rd, Pine Island, TX 77445, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.64386449999999, 29.7515036], "type": "Point"}, "properties": {"photos": [], "types": ["point_of_interest", "establishment"], "reference": "CmRRAAAAqXmuJvcTIuD9g7qVXFHXQdp8HMj8c2yKBtbrwpoOcaj7DFuyrvPSYbBBUxjeEHE9JaYIowKn5ujNf4xmjJ_ilnnLQscRoX5HJiFaUadm3glVtMJ12dS8WNyeHhhDjsG1EhCj_S5v45ovMMTq7gWO_CFWGhQ6FqOEZQYC2y6Y0hTnlsKZTbZQRg", "name": "H2O Conservation Technology", "rating": "NA", "id": "30c07988ef8dfc62dac712b9d587daa4a36f2539", "job_title": "Edp-Renewables-North-America", "place_id": "ChIJIWZRKeHKQIYRXxta3wOMGGc", "address": "1725 Hwy 6, Houston, TX 77077, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.5705632, 29.7714443], "type": "Point"}, "properties": {"photos": [{"width": 3024, "height": 4032, "html_attributions": ["<a href=\"https://maps.google.com/maps/contrib/108143329814504597326/photos\">State from Jake farm</a>"], "photo_reference": "CoQBdwAAADc9Af7xKBUGrttn8CuqbwUKUMxELCt7Lx2bfMQCZ_oHn_3Hs77FajqkwScUdt2NjtMzlY0QhdyBbBAW4FX-Iq7LoNtsdEiX-QNSz1UyOSBzFYST712xx4YM9O5HTLJwYmRvPvIfxrRKgnIzrNfmn-buyXVwnsrut2MdiiwJM89BEhBqQtkGuJPXSEWOcuWd-1z2GhQJHWNX7R1rc6I33EglgajYXXBMHQ"}], "types": ["park", "point_of_interest", "establishment"], "reference": "CmRSAAAAb-WfkTYR5_qhpdD3M3ZWxafqjpnhY2k0YmiyOLCaj_aV4IHzuK66_JNfSYBa4K0SHfK8Dnq-NCSYEtcLfeB_P57QfVloI3EEk1GX60CS3R_Dp7jem4cxnDUA6HByOTdMEhD7nG_z8W0o28jQu2rpTfSUGhRHuy1ZQAONmOmwsbfwGSCyzusIpQ", "name": "Houston Audubon Society", "rating": 5, "id": "050a5458d86bdd1cee7b09678bd6256d0a20a73e", "job_title": "Edp-Renewables-North-America", "place_id": "ChIJlQOxwVDbQIYR2uX_TZl0TYc", "address": "440 Wilchester Blvd, Houston, TX 77079, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.56820189999999, 29.770778], "type": "Point"}, "properties": {"photos": [{"width": 1800, "height": 1200, "html_attributions": ["<a href=\"https://maps.google.com/maps/contrib/108765250995932379967/photos\">Audubon Docent Guild</a>"], "photo_reference": "CoQBdwAAAHAoVqmKHJy5n0OKsfQEJAqr2NvhJQlDWU0c6cMsK_Oq6VHUYYSJ_hI7nJltMpfVK5K3Dkcw0KLpR-TgNOEbezFSL3eDECAZFr6gSLORJaa_1mM6lOH3vGGrjmDFPiJM-g6EFImvmal4FYxKQrA_DJzHzvvkttKJoSUT1hCHlscYEhA1FU5Ttp6s9zIwe2IOFu7TGhQJZ4lgjfBkT_kT4xPNXKFPrcU5sA"}], "types": ["park", "point_of_interest", "establishment"], "reference": "CmRSAAAA_lO_kemmnMAxhlMMr6pYHatVBqVm2IAO4mP5YcpEYTcPrr7gvlJEdYLfHpOds19L2pqiZnzRHsr724KhAprxMjZAwNfAYl5f3HvWxiSbtjT-aQiyFaK6uohRbDy4tqE5EhCOhW0LcrySpwu-7YDRu0Q8GhR7hKTYJLCaBdF9kSql2j_bWzfLDA", "name": "Audubon Docent Guild", "rating": 5, "id": "7ddd5daf76cc4979e2ba6b062322d1c77d5d1c07", "job_title": "Edp-Renewables-North-America", "place_id": "ChIJI9XyNFHbQIYRtwHb8EtTpeU", "address": "440 Wilchester Blvd, Houston, TX 77079, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.44932349999999, 29.7803218], "type": "Point"}, "properties": {"photos": [], "types": ["point_of_interest", "establishment"], "reference": "CmRSAAAAsd1OqMa0Pbl8pOfO5FXmeZG8sOrGCbxM6TnFh-BcgC6ZhIqr5Xay3s86jwnEdJ4AjuDXowlxToqqQS20b18f3aMZMBSmJcVgACBucwliz8vjSipfCzw3iC0V-Hd9ggb3EhA9bMfDL8-ucrcFjm_NJnMxGhRg_nKirDaDtjPcFaUGFbFXhHtIjw", "name": "Coastal Conservation Association-Tx", "rating": 3, "id": "7258b034e119f31e82320bca6e72781ee9f79d75", "job_title": "Accredo-Packaging", "place_id": "ChIJcekacM_GQIYRPzL13cgQrPk", "address": "6919 Portwest Dr #100, Houston, TX 77024, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.47039, 29.655454], "type": "Point"}, "properties": {"photos": [{"width": 5312, "height": 2988, "html_attributions": ["<a href=\"https://maps.google.com/maps/contrib/101184977609161362375/photos\">aug4</a>"], "photo_reference": "CoQBdwAAAPE962_YtGPDkjuVRU10KI6Iicfit0x8M-jxYklm4IZ6acnK8T9a0b8SjaySrRNDrKeBzG7On7cg6FACz9sJqRPRublLbgvERpk3E5RRaELvhhY4sd1WD6MdTD75FICcriWOFbJ-PEyIJZ8NM0u6Jdm0jaQesLUExekos-QXxK6xEhC5tG7X-J5U2b_B4Xt42w6wGhRAEcjsHwB-7TCkc33HVlxVt7glNA"}], "types": ["park", "point_of_interest", "establishment"], "reference": "CmRRAAAApjHQMDrMiIFB0LejohYkxjepT98THWSnxoCwWy8rx8OzIgB_Tn8FW9lGmoQx3tIh_QzWpjssJGWP26ZFvNN7-jZnjctVzAbnYK0fd8qr9MBRFFiGIPp7gka45_1GRdaLEhAzjUwgoImIApfyWqfVc30vGhT8kACFAwzHCgsPRiZhjo4bqGielA", "name": "Willow Waterhole Greenspace", "rating": 4.3, "id": "0127506e8071350c2d48f0ca56e939045297a0f4", "job_title": "Accredo-Packaging", "place_id": "ChIJR6_2zTzqQIYRsA7wExgfDWs", "address": "S Willow Dr, Houston, TX 77035, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.4003322, 29.7388505], "type": "Point"}, "properties": {"photos": [{"width": 1136, "height": 640, "html_attributions": ["<a href=\"https://maps.google.com/maps/contrib/117056878997299689379/photos\">Marisol Brown</a>"], "photo_reference": "CoQBdwAAAJXx7--eq4cRSZqNE7My-YN7ft4Ky3__N2lWtxx5eTCQWnp7ObSMuvXPK31hs-5nC_Bih9Y8pJ8zAFTI-yu-zx1oENwAL3hAYsjcXyzUal0vS0gcqUVOFYDnnjIMzplaceOTKLJxkEHcs7sAJsqu3xy9wWADMqpZO8pTBm6lxrVNEhD5Au-D1rv-VECB9DBnAotWGhSOsXyCKBTuNnyBliOtHU3MEUAbBw"}], "types": ["point_of_interest", "establishment"], "reference": "CmRRAAAAAwIm9Bn7NHF07FRe9o8ysVVSvMSYftKVs78LNgOwHQwq120d09udMKkLg-E6kuDrkMeE0QUs13ymMrcLZFb4N4F0yK5juA_LPPZr2YCr35HcHjQtXaC3wd52uzy7Vpk6EhAFxvuv_TxgF72LfZzGdpHCGhQmvoH3oH7jy6v1nQluMANhHAwwTg", "name": "Masters Fine Art Conservation", "rating": 5, "id": "a462c2eef4e22ea319485ae7b84f3d20756cbdd1", "job_title": "Accredo-Packaging", "place_id": "ChIJp8u2bZvAQIYRbosnWz6cVmY", "address": "1612 W Alabama St, Houston, TX 77006, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.3876169, 29.794149], "type": "Point"}, "properties": {"photos": [], "types": ["art_gallery", "point_of_interest", "establishment"], "reference": "CmRRAAAAvC5YKZGfW9MpBuBHvlVxzukmnYh3wBiIwloAvYXNrmVtXT9KSx3xR62VNN9sBJdQGqvWGu5QOcNlc0iUMzBj2neJsVEfwwxcnhO5tmZkfV2JJl-SdYwRZGaRXGcqwrP3EhCBCSpfncw4R2D1mfYMISB1GhTwglA_PUKGrhRYjnkHLchMCD57zQ", "name": "Whitten & Proctor Fine Art Conservation", "rating": "NA", "id": "883a8c5ef35ab28e1630235ad65a6b16506a67fa", "job_title": "Accredo-Packaging", "place_id": "ChIJ8YuXE6K4QIYRn1SF1hazFEw", "address": "1236 Studewood St, Houston, TX 77008, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.3858767, 29.7300997], "type": "Point"}, "properties": {"photos": [], "types": ["point_of_interest", "establishment"], "reference": "CmRSAAAA93NTR8H8l_tvHXoCCkwtBGgha6PlyWfNkZ8UPYlcJpZ8Qvjv0-2x7avitq2cCuKApeIgAD0PRCi3M9xWMi37pByVoSzLQfYRaZWsHzopoMEky66QBZwPjzg6QDFLPgf8EhDkX5AISYh4xo91g0O8tXXqGhQE3Iu2_VlN-cAzpBVpppJcg_pSsQ", "name": "St Mark Fine Arts Conservation", "rating": 5, "id": "ea2d4bac6d74716b33f456dff3aae0cc0b43cca3", "job_title": "Accredo-Packaging", "place_id": "ChIJKbDEoXm_QIYRcRFBlp0dE8A", "address": "4901 Main St, Houston, TX 77002, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.483218, 29.7482286], "type": "Point"}, "properties": {"photos": [], "types": ["point_of_interest", "establishment"], "reference": "CmRRAAAAkOfRjrDuSF_MW7YAwZW8xhaO-4EehH_15Qkeg0iZSHnCiXJiOzgyEQJLX28dv99Lhfz5e2Bf9HO-PmJKSw6FmD1iYT-Z4_M_xJUajGsDSUu-S1yoUCcdoFC1PsWobkhYEhC9G4dnoEU2BJjqE-dzXxGyGhRC5nqDg8kD9fyXHKQlI6e13CQpBg", "name": "The Nature Conservancy", "rating": "NA", "id": "90af6fb9fb926dde9f7103577cebc4150bbb1dec", "job_title": "Accredo-Packaging", "place_id": "ChIJq-m4EX3AQIYRJkn4Lhccp2E", "address": "1800 Augusta Dr #240, Houston, TX 77057, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.42318089999999, 29.7345943], "type": "Point"}, "properties": {"photos": [{"width": 750, "height": 437, "html_attributions": ["<a href=\"https://maps.google.com/maps/contrib/106788706324997826205/photos\">Erika</a>"], "photo_reference": "CoQBdwAAAGD-ZHKb_9nnK0si62-E32B4Vik9htb6_w3kyIPfZ2-NTjzfG6l7mAUuPajem_o1RH6xOV_HIMnyvdNBTt8Ct4yubzdkrp41Jsf3gSWJXwAJ9Rv_pwvAf75oXhbtbFdzO5NkmivME9fDj1nw709Upy92wT6BquG5q0QCedGvL6W-EhCOmc8miNOSv2e-mVF7bOnYGhQ7MIx_K7Mn9iXKndEQrgonBAbcEw"}], "types": ["point_of_interest", "establishment"], "reference": "CmRRAAAA-KrZ7wFk2oBU8OlFBP8NewBnJGaIHxXVHhzvfQ44RlGSNvAREAgg9re4CU9GYlUAAJLUbaRauUGgh7LBhoisVFUnyUKxU3nPongx9EXp1D__I9ESlrdDr-MIoltaAGxmEhCagJgMLtxxH5VQ9Ojzdk7PGhSEI27wM3-cQfVBZCJFIaiyOkzRfw", "name": "Student Conservation Association", "rating": "NA", "id": "1c5ea7722fc0d99e9f7dfca55f5d9078224d51d3", "job_title": "Accredo-Packaging", "place_id": "ChIJQcqBXfDAQIYRErawO-goGj4", "address": "2990 Richmond Ave Suite #400, Houston, TX 77098, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-96.038102, 30.055621], "type": "Point"}, "properties": {"photos": [{"width": 984, "height": 985, "html_attributions": ["<a href=\"https://maps.google.com/maps/contrib/110279808588468038448/photos\">Peckerwood Garden Conservation Foundation</a>"], "photo_reference": "CoQBdwAAAONOjEP3B2X1GDQtFdWWkxNBgJgb4UrnTR92myZYEdTsI-dGZEFaXMMDQm6S7mmhDFL_grxuJCZ1GmBnu5Bs8PqoCRTgl3ZeZBLbxOwpfsfTqgrOn1UZvdtHknXU4AUx65V61TfPlgRAEcgh-ZQN17VL50hIvXwS-FH1o6cJOItXEhCgTwUmVkqKod8vVe1SfbIGGhQs4tvZ5q_QZzAnfo90w9YsnZkUQA"}], "types": ["park", "point_of_interest", "establishment"], "reference": "CmRRAAAAc5YZnt_GiqZEw6k3KooSLsEDAxSAopcKKjLTbfuhngF1fBp4oNauTFni9TlSUX_eMbDLiAKQTPndjJmo7vRBuvxZyg-wTPp8xM4v8zJfwVedKLZ7rmkSElZIPELFqjuFEhBExiuwCXkl7GM2IUH6Hsv5GhRm47LIcuZU6oB36CT0wHFbttGK0Q", "name": "Peckerwood Garden Conservation Foundation", "rating": "NA", "id": "e618a4c618cd67ce4f5fdc165f640220ab3b53b2", "job_title": "Accredo-Packaging", "place_id": "ChIJmUR7pvHKRoYRIIl0o73bPGE", "address": "20559 Fm 359 Rd, Pine Island, TX 77445, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.64386449999999, 29.7515036], "type": "Point"}, "properties": {"photos": [], "types": ["point_of_interest", "establishment"], "reference": "CmRRAAAAzSwJn2ltpOMdwLOh_SKyruVyREPOI-lOpVs5z5TTMtIRAMquaHMDm4XQh7Ygk6kfbDLwbBUD7wRUBKfmB3eBSKX_-0bepdXzRuauYzCLJL30IoOU09DnhJ_6KipR1FyFEhCkuEbOt0Snlwb5Hc1X-rONGhSOkU9NEoDuRevo4txgPkJCsd_rrw", "name": "H2O Conservation Technology", "rating": "NA", "id": "30c07988ef8dfc62dac712b9d587daa4a36f2539", "job_title": "Accredo-Packaging", "place_id": "ChIJIWZRKeHKQIYRXxta3wOMGGc", "address": "1725 Hwy 6, Houston, TX 77077, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.5705632, 29.7714443], "type": "Point"}, "properties": {"photos": [{"width": 3024, "height": 4032, "html_attributions": ["<a href=\"https://maps.google.com/maps/contrib/108143329814504597326/photos\">State from Jake farm</a>"], "photo_reference": "CoQBdwAAANM-9CBlPDjVYwVLaI4V0oXFoHcgjU7VjVCteX7cTvQ8947ykppm30oAKPJYbRYju4NXy6Xuy5AeUcainX4G0hX6EhsH-a0eRIYuibdIPYRAnVhDTstvYYLE8axv_jbIA3-Ynbe0poVT7WIdTGTlD8NPhNGnTunNBgSVJfx6UYwFEhDZ4zOfrrXjmuYzJ9e_eB6dGhQCSd3hL7J0T3_5qQzGhPMwfIThPA"}], "types": ["park", "point_of_interest", "establishment"], "reference": "CmRSAAAAuXeO4H7evewZkdCtZpnDZFq_jBDvHp3bCNx5SSDNXCjRZaSdflT46RlZu5b1Ves-YNj7Zl1lXeJhY2_v8Qr1V-VExV0Cxh2hqCTMS6DF-_ElpzXLW9e-U8j4L_yxXKo-EhAdpcJRImPsDinG9iawcLLwGhRfUAFRj-hoAMZXSxQglQJHVC4afg", "name": "Houston Audubon Society", "rating": 5, "id": "050a5458d86bdd1cee7b09678bd6256d0a20a73e", "job_title": "Accredo-Packaging", "place_id": "ChIJlQOxwVDbQIYR2uX_TZl0TYc", "address": "440 Wilchester Blvd, Houston, TX 77079, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.56820189999999, 29.770778], "type": "Point"}, "properties": {"photos": [{"width": 1800, "height": 1200, "html_attributions": ["<a href=\"https://maps.google.com/maps/contrib/108765250995932379967/photos\">Audubon Docent Guild</a>"], "photo_reference": "CoQBdwAAAJU7IMRozMnWm3w9IZ78ya3RBxpon8c8ex0gi9ECLhTrvbdBs91_t6LzKeFHVkg98aLFvcSWNZPCFn_k21qT7S-_epkYFHO1SYcSyMf1ZOXqum4z6Co6_2vHGg-8kYQhghp7-9W_Ep7knDp64VqbeoQ6LUnAualk3Z1g55RRpt-iEhAS9mYT799MSuaFsqXQaz7oGhR_atDr4GkTEg8nPbAudRthG-LewQ"}], "types": ["park", "point_of_interest", "establishment"], "reference": "CmRSAAAAZb1KuMorF4FCdryf9FqFowe3b0jQVDY7k_g8ismJeqN8u2y6NQjcGki7JlgLiPIrkFEj9gqzwVK0r3UUnyfUaxtzRsOQbtXCqfduIfsLYDIWZ6tItZzSi-vlI4AIVTTxEhCwuRoUyBgFbvH1Q3Q3KuKOGhSFC0jrnFLHTuP3ny1s6TSRi6yuGw", "name": "Audubon Docent Guild", "rating": 5, "id": "7ddd5daf76cc4979e2ba6b062322d1c77d5d1c07", "job_title": "Accredo-Packaging", "place_id": "ChIJI9XyNFHbQIYRtwHb8EtTpeU", "address": "440 Wilchester Blvd, Houston, TX 77079, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.44932349999999, 29.7803218], "type": "Point"}, "properties": {"photos": [], "types": ["point_of_interest", "establishment"], "reference": "CmRSAAAAAiJUoyqBFumE656b4ug7tanw1-5Ih3ZMd6RKlseb_6LsTPtjg9iqeoXWuv8O0azPfEZZEzKCxJHv0pKxj8ZWnECDPQNWOOsbw4RQ0f6gjmrKoI3Bo2pgGuaNQWznJk0JEhAsVSp7t2Z_3HpcSROHHoHWGhTHxRQeEKJ5gzk4bi46ZlR6Chqo9g", "name": "Coastal Conservation Association-Tx", "rating": 3, "id": "7258b034e119f31e82320bca6e72781ee9f79d75", "job_title": "Memorial-Hermann", "place_id": "ChIJcekacM_GQIYRPzL13cgQrPk", "address": "6919 Portwest Dr #100, Houston, TX 77024, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.47039, 29.655454], "type": "Point"}, "properties": {"photos": [{"width": 5312, "height": 2988, "html_attributions": ["<a href=\"https://maps.google.com/maps/contrib/101184977609161362375/photos\">aug4</a>"], "photo_reference": "CoQBdwAAAF4WNxJQb5eGGPGhRhCYzkbc28wzy5iF53tNS9_dztyDL16L-galbHcjILvga_wixRQCVP3yBRdYoX39qZiVwmHh8d8uBAM85OhGaRmXRVI2ISMFP4I3gCbUs2KWUaGcxCJLC1ZAwWIx68bBS7yeAToC2Sw5HhiQgQAshcAA3M1NEhCWgUwxsIoWGfkiiq8aokWiGhQp_OTNLwNH8h1XUsDFlWpcYXY9cA"}], "types": ["park", "point_of_interest", "establishment"], "reference": "CmRRAAAA_jL1sxCs8GKbJRNTM3C4KwjMeiwDuYLsrFiqJjddoMaSW3n3WI2ZXtLOvcBXop-eICkmEZuJuxczyEBfrGaSQXKTmTAk8likUQqinTr5aDINr00OIAOEwACgpc_PLxsYEhDJb1-sZB7O5a1LUCh9Gl3xGhT2zoNQGH12aMrtarJJ_2Fdb6HyTQ", "name": "Willow Waterhole Greenspace", "rating": 4.3, "id": "0127506e8071350c2d48f0ca56e939045297a0f4", "job_title": "Memorial-Hermann", "place_id": "ChIJR6_2zTzqQIYRsA7wExgfDWs", "address": "S Willow Dr, Houston, TX 77035, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.4003322, 29.7388505], "type": "Point"}, "properties": {"photos": [{"width": 1136, "height": 640, "html_attributions": ["<a href=\"https://maps.google.com/maps/contrib/117056878997299689379/photos\">Marisol Brown</a>"], "photo_reference": "CoQBdwAAALXbGkj94DKQxGimc-yyW8mFH1NvOSCC-HJeZTOtyPgcBKCrLjRVX20j0VwRUePGqgZKBg9pA8jRw-56kMuKtBP7pA0mcZtKryO2QIgcHjoXuP-O5QqCg5dCLo6VmfSG5rGzvXdnqWkrN4x_fBjjtqB1GqkUqqSzz7omhxOoj75EEhCFskBry2k3kYxWXzOdFQmfGhRgNlXm02V96OSsH6aCoJOVhaF0qg"}], "types": ["point_of_interest", "establishment"], "reference": "CmRRAAAAc38kSe5VIik53nisheR4tlynNAZpPpobyPEDMQHKwVkzMCqwJtIGGm0lKTU_K_Qe3lUzlNytIz72iiVtZRoTz2IxE_dYGXrDjDG2nxDeIMD2mRIsXMujpI1q_bX0sE3aEhBu_3f43gKyILt_zqbf5HDAGhQtYf6nrITCyQBPA36Lh8nKoleUWQ", "name": "Masters Fine Art Conservation", "rating": 5, "id": "a462c2eef4e22ea319485ae7b84f3d20756cbdd1", "job_title": "Memorial-Hermann", "place_id": "ChIJp8u2bZvAQIYRbosnWz6cVmY", "address": "1612 W Alabama St, Houston, TX 77006, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.3876169, 29.794149], "type": "Point"}, "properties": {"photos": [], "types": ["art_gallery", "point_of_interest", "establishment"], "reference": "CmRRAAAAUxRJihFMRgTz8-v3H66CTxyujS74oFyIofEgvYO8Cxby7y43GLY9Zqq2DqijGVAH0pIpzYOw_Jka1s2WYDGCvhF0vTduUN7hIvfbFIpF_PNrwRX3psBv2DahILHww9uGEhDO-nr9Birq9dupgfMelbJlGhTAkRf2LIUR6QYh8CzMz3YlDEvrMA", "name": "Whitten & Proctor Fine Art Conservation", "rating": "NA", "id": "883a8c5ef35ab28e1630235ad65a6b16506a67fa", "job_title": "Memorial-Hermann", "place_id": "ChIJ8YuXE6K4QIYRn1SF1hazFEw", "address": "1236 Studewood St, Houston, TX 77008, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.3858767, 29.7300997], "type": "Point"}, "properties": {"photos": [], "types": ["point_of_interest", "establishment"], "reference": "CmRSAAAAaABkDuDBMr2aojwUp8iaXnHucQzkXoE5wO__kkB-Po0MkgmKnOoQUnubka3a7YQ3QeyJkIWrtEXHe-WEDQxyzCKwSbDRANAhrKayBXC_QjeG56EZL8Q7pNuKQl9Hs1zHEhDGudICCn6qEybfrn_P6BWMGhQ8Hp8IgpdrTsA_ha9ixH3Pm-PiEw", "name": "St Mark Fine Arts Conservation", "rating": 5, "id": "ea2d4bac6d74716b33f456dff3aae0cc0b43cca3", "job_title": "Memorial-Hermann", "place_id": "ChIJKbDEoXm_QIYRcRFBlp0dE8A", "address": "4901 Main St, Houston, TX 77002, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.483218, 29.7482286], "type": "Point"}, "properties": {"photos": [], "types": ["point_of_interest", "establishment"], "reference": "CmRRAAAAzY0mw2_W6Cou4vGiSyIK1zNuLJrdC76yDkhZc495rX9fs8yRlkJBI0SP-MXjZh797DqWXC8rk7f5m5wSwuBIg6gPVzHZ-fTx9kfN-P5L8VlEJ3JxTbILh6hvWUQiU8XEEhAKbozFymdLtPvcwd0IZdl8GhS-FH5B7aM8wFXAYsQchhT-bhvN7w", "name": "The Nature Conservancy", "rating": "NA", "id": "90af6fb9fb926dde9f7103577cebc4150bbb1dec", "job_title": "Memorial-Hermann", "place_id": "ChIJq-m4EX3AQIYRJkn4Lhccp2E", "address": "1800 Augusta Dr #240, Houston, TX 77057, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.42318089999999, 29.7345943], "type": "Point"}, "properties": {"photos": [{"width": 750, "height": 437, "html_attributions": ["<a href=\"https://maps.google.com/maps/contrib/106788706324997826205/photos\">Erika</a>"], "photo_reference": "CoQBdwAAAFjhruenwFKju91GMr732FhL3RciPQmDOo23NT4sth38iQ4KQB_U-PSueYs0jvspLMUzxzFX6cXdYy24yMMFIx0TiAc9bfEyeOT90bF2imL1vFduUpDaqRZIwD9PnXJvNgay0BoCaMNO8JbLCm1-PG0RcNAVnSSwlKuvqW3uHQ69EhAp9Sg_QcJ-jDmGdp-sDmkoGhTZfalKfKHN43hBaVr6_ijs9VUGlA"}], "types": ["point_of_interest", "establishment"], "reference": "CmRRAAAAJaGQvwdPGfDI-ezxoWSB0foeFSWy0odBgjgcncRK_GmbU8jpiNXkzB8C_srgq-nUcWObcSsPiLLiITvsUJG-Vw4L6KMzZPDgKnpXzoSI3Er7da2gY0YQ7Ih_u7DWdgpWEhB9KvvntwMHpHnK7etAUxJ7GhR20bWGxkl5h6RQ5F7P_iL3WWw2Sw", "name": "Student Conservation Association", "rating": "NA", "id": "1c5ea7722fc0d99e9f7dfca55f5d9078224d51d3", "job_title": "Memorial-Hermann", "place_id": "ChIJQcqBXfDAQIYRErawO-goGj4", "address": "2990 Richmond Ave Suite #400, Houston, TX 77098, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-96.038102, 30.055621], "type": "Point"}, "properties": {"photos": [{"width": 984, "height": 985, "html_attributions": ["<a href=\"https://maps.google.com/maps/contrib/110279808588468038448/photos\">Peckerwood Garden Conservation Foundation</a>"], "photo_reference": "CoQBdwAAADGdOYV7rXz1EB4LpUa_bvsuhOPRGmHJrcHJX9uwuoTDK39vml89HaDrgnCzDQ8KtpE5Gc-KtMQqRLUsdt4BFZm5Xjp6ACeNgZLYdH9siW1R_TvqZZH08kDM7P9PIx1e-FyFudXNPwNiN7UViMlCmkbesRQJFxFXfADI4T_zWFj4EhDofxdxVUkL-xmezeA9yty7GhSsITYneirHxL_EfgIQakhTVXmJPQ"}], "types": ["park", "point_of_interest", "establishment"], "reference": "CmRRAAAATdWqrhnO9TCcb0VcBrHv0ZhtUc_fFmEexGPyMJiM-DRm1S4NXnGZiLvx1LDxQkrFDV2uTiBzVwPIDmRrxcDaxKgt4Y_6gPrF1todfX5BJQRzVzzs51jILfkkrzR-TI5OEhBEfEnlPE1yd8CnAGohSB0-GhQOzqwW8ARvIcWUHz7Gs_OP172hSg", "name": "Peckerwood Garden Conservation Foundation", "rating": "NA", "id": "e618a4c618cd67ce4f5fdc165f640220ab3b53b2", "job_title": "Memorial-Hermann", "place_id": "ChIJmUR7pvHKRoYRIIl0o73bPGE", "address": "20559 Fm 359 Rd, Pine Island, TX 77445, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.64386449999999, 29.7515036], "type": "Point"}, "properties": {"photos": [], "types": ["point_of_interest", "establishment"], "reference": "CmRRAAAAUnwuLpqPcLGcayL3iCRs0-G6bocZkqwIZB2FhY1KEEJwmsIDQflEpc59P7v-etKiaBUhztmPeQFaSe-82qq_WRICpY00KN6zvtkJL2QvaHoaF4tu2kIY8cV2e0QtDL7BEhDEk-vnRVXDLQvjodhC4CtaGhSdUTngSaZLclGaluW18YmxSI6Tqw", "name": "H2O Conservation Technology", "rating": "NA", "id": "30c07988ef8dfc62dac712b9d587daa4a36f2539", "job_title": "Memorial-Hermann", "place_id": "ChIJIWZRKeHKQIYRXxta3wOMGGc", "address": "1725 Hwy 6, Houston, TX 77077, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.5705632, 29.7714443], "type": "Point"}, "properties": {"photos": [{"width": 3024, "height": 4032, "html_attributions": ["<a href=\"https://maps.google.com/maps/contrib/108143329814504597326/photos\">State from Jake farm</a>"], "photo_reference": "CoQBdwAAAADkPzuATCextohfcNIFUcQrX9EW1SRPvudLlfe4lG-lbk4FhVHCwj9qhahSh0qBQ5FQJg-0akkh-HqhdkpXPjAPAihEYFfanIfEx5KqwvNke1U-I2JyBGVAfYrSTjStqjDbUnOVX7jvdq5y_wP--C9kdvIz3SXmJBo-6Lef30VyEhCQdBYYeZkhBlu5pvWj5bBrGhSENnusDL9D7IvxxXjflDlUzG1nCQ"}], "types": ["park", "point_of_interest", "establishment"], "reference": "CmRSAAAAnoclwm9XvD5137W1kv4O-nPOPpoAVH_tEMu2s6mJYPL5NZ3t2KIsus7fsU6BkDHPmcKFysDmZmZ0uyD0qRJaJUec2KS1mYjz4y3d_d7q_CWYiEy3-YkEHa-RnKMugyTPEhDiPOx5XyDFbO2oEyDiV2bbGhRGd6KOtFtAe-aH1QtZr2R66e8WBw", "name": "Houston Audubon Society", "rating": 5, "id": "050a5458d86bdd1cee7b09678bd6256d0a20a73e", "job_title": "Memorial-Hermann", "place_id": "ChIJlQOxwVDbQIYR2uX_TZl0TYc", "address": "440 Wilchester Blvd, Houston, TX 77079, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.56820189999999, 29.770778], "type": "Point"}, "properties": {"photos": [{"width": 1800, "height": 1200, "html_attributions": ["<a href=\"https://maps.google.com/maps/contrib/108765250995932379967/photos\">Audubon Docent Guild</a>"], "photo_reference": "CoQBdwAAAElbwjEMwUMD9K6k27HJrqAoSUUOKYW9WXOMGNwTlkOOeNqXuWsBhPL3eGcQL-0mNMfy-IDNI1ihVDnJvvkIwmEIRA-F0Va31AV1CehL5zkrbo88FUi9oMrkGajWAb9hcA4XxX477d8GjRYvPiSiS308IyRZ3WQ-0vWXGejLvNeEEhDInOFmdHZT-E190hzfmgVCGhRh4mXb-BuH4mPQ2s1y_0HhxoBbWw"}], "types": ["park", "point_of_interest", "establishment"], "reference": "CmRSAAAAQHSuTf8_NvgVzIaRVY0dkGUhLGf1yJtpIwAeWszhAJO2uCSExrVlSDlZ1xIJ_KB3V0dHgeBtKutokRKTAvXrMqwfhX_8LxLU9pli1xEsqJm1Q_zXqcyGEH-o8A3sA2B2EhAuxSJqKRaVlHFjZBf_2CkoGhSMn_E309RjE1mRbzJhgjCQT9oNuA", "name": "Audubon Docent Guild", "rating": 5, "id": "7ddd5daf76cc4979e2ba6b062322d1c77d5d1c07", "job_title": "Memorial-Hermann", "place_id": "ChIJI9XyNFHbQIYRtwHb8EtTpeU", "address": "440 Wilchester Blvd, Houston, TX 77079, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.44932349999999, 29.7803218], "type": "Point"}, "properties": {"photos": [], "types": ["point_of_interest", "establishment"], "reference": "CmRSAAAA8Z5UB7tukwiI85pA8XDDX7Znn2PD2uPuEtAqjObRw2nyMtaVyw0cUfqLf0PoMVcI3R07dIaY9O-A-nvwo5GQFSqlV_optGSLRuPWbfCBbQLPw530ExCaAYPUynHeRMRJEhAjCGnQvXQ4gzTAbWAAut7PGhQDQCbFVxIdzIei6lQu9pd5HXzeMw", "name": "Coastal Conservation Association-Tx", "rating": 3, "id": "7258b034e119f31e82320bca6e72781ee9f79d75", "job_title": "Ch2m", "place_id": "ChIJcekacM_GQIYRPzL13cgQrPk", "address": "6919 Portwest Dr #100, Houston, TX 77024, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.47039, 29.655454], "type": "Point"}, "properties": {"photos": [{"width": 5312, "height": 2988, "html_attributions": ["<a href=\"https://maps.google.com/maps/contrib/101184977609161362375/photos\">aug4</a>"], "photo_reference": "CoQBdwAAAPknmXYxTqyolQYLFtJ3kJ6AFFVQBYKa5KBP25ji5aTJGZju8-Pe6qzmPGr9o1n4jVPUtQYXYwt_sZdJbmUx1NdAlljYzzLOPzgLhO1WtJEGTFpojyIapriPn_8BZKxGcmjy1uxSs_QS58JmCY0AYX3437s7bixe7LkQzglWotFqEhAJ6zxG0AI_Hy2HzT3tje-uGhRFGQqdUId7c0ms66llKrAYy5-xog"}], "types": ["park", "point_of_interest", "establishment"], "reference": "CmRRAAAA0qCQ7wzwQVljHCzSTPd-1hp9v_5ltRLDVcabNQlS0hvEYUdIeN1k5crjFXanY6wIvrrLOTcQ5L-8X-pYJX0oeq4Nhj2Qk0-cHddI4AnNEFXHwvsYVp6ZUzmP9doVkVkaEhCtRE_XuzowVz1L4l8zP0OYGhTjEpMc2Tit8bQ9wTr5lxEM4JzmWA", "name": "Willow Waterhole Greenspace", "rating": 4.3, "id": "0127506e8071350c2d48f0ca56e939045297a0f4", "job_title": "Ch2m", "place_id": "ChIJR6_2zTzqQIYRsA7wExgfDWs", "address": "S Willow Dr, Houston, TX 77035, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.4003322, 29.7388505], "type": "Point"}, "properties": {"photos": [{"width": 1136, "height": 640, "html_attributions": ["<a href=\"https://maps.google.com/maps/contrib/117056878997299689379/photos\">Marisol Brown</a>"], "photo_reference": "CoQBdwAAABSbV81rt-7ldYVtCRopLojQ7qSIbh3xwvd_14QmW1gJLJ08GHOJhFN3yFDX2CLXd8i41NtReFLlr2bVzfYWnxdxIL-aa0gGAd3G2Fwo7sU5eqrcGCUWO_B-ctcEY52VfT8fM8KPrt73d8eVEaihudb-Y98TniXkxsJbJOYZ5_89EhDva8cCa6FNS8OdJMeah1vfGhQKoTXTrbZjFYvjymbSUhHgvko6LA"}], "types": ["point_of_interest", "establishment"], "reference": "CmRRAAAAUjPoh0nIFHHIRchu4rwSZOn4sAypTMrEWlGsKPJSspGmmQWhBvAGl8aJBUFvo4Szuvh1KixAdbwdlP8LiARG8LWx7CP1KYgK0BMTINaH0BX6EAMXGPwKrGgEJ8l6eqTAEhC1RTJfvXSuMgZu8nGO6u6vGhRw9mY8dnXM87g5r_JnMTawtKPWQA", "name": "Masters Fine Art Conservation", "rating": 5, "id": "a462c2eef4e22ea319485ae7b84f3d20756cbdd1", "job_title": "Ch2m", "place_id": "ChIJp8u2bZvAQIYRbosnWz6cVmY", "address": "1612 W Alabama St, Houston, TX 77006, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.3876169, 29.794149], "type": "Point"}, "properties": {"photos": [], "types": ["art_gallery", "point_of_interest", "establishment"], "reference": "CmRRAAAAMnXDgdykpFCPMSf_Vl6uts_7WaWAuaHJ7BD2t-54VSRRYEpaS7it-TWinrvHgKFELQvNBYDDilLtNdqaS3Qb4QTvm0MrgEkET1IgBFwVz4Rs1FVvFadHJZs5SqmGzQ9AEhBC6gzFU6P3Mra0sUTZiuMJGhSJUDp8wDVwORerNyXSMuP5fhaunw", "name": "Whitten & Proctor Fine Art Conservation", "rating": "NA", "id": "883a8c5ef35ab28e1630235ad65a6b16506a67fa", "job_title": "Ch2m", "place_id": "ChIJ8YuXE6K4QIYRn1SF1hazFEw", "address": "1236 Studewood St, Houston, TX 77008, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.3858767, 29.7300997], "type": "Point"}, "properties": {"photos": [], "types": ["point_of_interest", "establishment"], "reference": "CmRSAAAAi78t5dtZcvc1n6N315M6i4GGLG4d_-0mdOXQJ6CCBISdQtiup4OiPipwTEETVs6CC_Y_PtXJFKShtiMqyiWlvKhg-5gJh21vQm_NdyZphp2Nd09xZN2ejU56qS1gGCYEEhC88VnqE7pbu1vc-w7_m3RzGhRk4kz_EnNuC640eXu8_4C825GAaw", "name": "St Mark Fine Arts Conservation", "rating": 5, "id": "ea2d4bac6d74716b33f456dff3aae0cc0b43cca3", "job_title": "Ch2m", "place_id": "ChIJKbDEoXm_QIYRcRFBlp0dE8A", "address": "4901 Main St, Houston, TX 77002, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.483218, 29.7482286], "type": "Point"}, "properties": {"photos": [], "types": ["point_of_interest", "establishment"], "reference": "CmRRAAAAD8MXj_DWhpITGDSyBMGLtsodpAwd2pX3-KEew-vVL20iudJuos13vI9pN5H0-RnmnCevDp4YJMUFpS93okgwZkJTEu4upWDLB7mqFXsl-lDJl1s0MoJu4z9eZ9VNB7hiEhB478kldsoKCR_YcjRtHMsVGhRrD0KJ959mcnfC92C2Q786KTgLUA", "name": "The Nature Conservancy", "rating": "NA", "id": "90af6fb9fb926dde9f7103577cebc4150bbb1dec", "job_title": "Ch2m", "place_id": "ChIJq-m4EX3AQIYRJkn4Lhccp2E", "address": "1800 Augusta Dr #240, Houston, TX 77057, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.42318089999999, 29.7345943], "type": "Point"}, "properties": {"photos": [{"width": 750, "height": 437, "html_attributions": ["<a href=\"https://maps.google.com/maps/contrib/106788706324997826205/photos\">Erika</a>"], "photo_reference": "CoQBdwAAAGgcKfJ2twPxGymctHsypSSSz3Je5_zS8mYvRbPetXTCOzzRct7-t6X4oz7E0wsj19ceGfdcZMBNfWheqNvd4kkn0KU42h6eikEWRV319kUMs6PGT6NqUwJF57usUZSuD1J4t167MIRamvuhAC5-oRx2uynZ3BOdqNquSXEvsce0EhDh_4HM53-GQQB23uIqueMYGhR_wjuN56jZpoHwm6qbwzdJQCrdFQ"}], "types": ["point_of_interest", "establishment"], "reference": "CmRRAAAALwwSJyJYr6hr9BZ5Vn4nI4--3tkUunT2Wmvhg3xFi7loxzcnRYDvpdQhlmaQIDW0DqObPWP-mscOSFCiv_Ym558JdLQqldEZhFFXqJ8sa_klJre4qx3tslYhR3uEV1_ZEhCX48hqc_xY34We7XBUK940GhQTxY3bSnXbGxJ27YRa4dc_W2QYWA", "name": "Student Conservation Association", "rating": "NA", "id": "1c5ea7722fc0d99e9f7dfca55f5d9078224d51d3", "job_title": "Ch2m", "place_id": "ChIJQcqBXfDAQIYRErawO-goGj4", "address": "2990 Richmond Ave Suite #400, Houston, TX 77098, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-96.038102, 30.055621], "type": "Point"}, "properties": {"photos": [{"width": 984, "height": 985, "html_attributions": ["<a href=\"https://maps.google.com/maps/contrib/110279808588468038448/photos\">Peckerwood Garden Conservation Foundation</a>"], "photo_reference": "CoQBdwAAAP6mBHgrX56MAKisZ0Zu9HlZTq2usDUdPGlZHvzNa8bXi9OtzIGDfOhdcgne_1LAVFdicGlsOIZIbhTIFVPzAn9Jb4Z_RhpIgH48A0sjR9eGUE2BWicpOaFqMiejbFkrlZ62mmf5CZUHDOLgZdoCFQzKlvcqE3WNXrbrc8KRFRT-EhDtUIXgwEqlCETsr9t-lhNeGhRIbwiwFI7BcO6yZUCwAnY11w5hOA"}], "types": ["park", "point_of_interest", "establishment"], "reference": "CmRRAAAA44rfBJBT1RF9mjET1lgCZ7WqE7DXX2fA8ZYm0kMnSdgtRtiw_tCUxMkEQY1jiDL45GftU22DygPX6qEe35XK95z36a-yWXiOwL_92tB5qmXpFVwCTghsSGnp7fwnWngMEhAR_P-huhVgCjpoADaOFdokGhRaLv8ryoFBaB4rC8kyY6D6vLzpXA", "name": "Peckerwood Garden Conservation Foundation", "rating": "NA", "id": "e618a4c618cd67ce4f5fdc165f640220ab3b53b2", "job_title": "Ch2m", "place_id": "ChIJmUR7pvHKRoYRIIl0o73bPGE", "address": "20559 Fm 359 Rd, Pine Island, TX 77445, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.64386449999999, 29.7515036], "type": "Point"}, "properties": {"photos": [], "types": ["point_of_interest", "establishment"], "reference": "CmRRAAAA8J4e_KUTLbTzs2WWOf9IK9cJ3pYnak5n9rI4u8nsAiJtOu-xGYlbatSsmjW0mZRtuwrHAvxrSNcUkKFCoMoa5XEicAvABADXShUI-5ltmrXDIGuDNkNBmeyiAKNg9ZCLEhAFC96YtC9Lb6odQFBadMiIGhSArICXSuUAe8FcILf_khYeCGwKgA", "name": "H2O Conservation Technology", "rating": "NA", "id": "30c07988ef8dfc62dac712b9d587daa4a36f2539", "job_title": "Ch2m", "place_id": "ChIJIWZRKeHKQIYRXxta3wOMGGc", "address": "1725 Hwy 6, Houston, TX 77077, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.5705632, 29.7714443], "type": "Point"}, "properties": {"photos": [{"width": 3024, "height": 4032, "html_attributions": ["<a href=\"https://maps.google.com/maps/contrib/108143329814504597326/photos\">State from Jake farm</a>"], "photo_reference": "CoQBdwAAAMlEhZQj1juH51sliGbWvVvSAQuqbsE3jp189nZSKn1dnVQCz7MBG5cPOggPzGiD1RVfvfwvMH3tL_ahPZv-pN2BDt61HJw5Mz6pHMIctj7DkjiSVuxwJvIygjsfrQK-O8nOSaKKeQK0MZuyPQagPdr2s19QlQTnCf3IhI5XIgtYEhAtu-JBWBeuaChMzuDES2lDGhSD_5OLFOoBOqq3KH1ilOFkA2SEMw"}], "types": ["park", "point_of_interest", "establishment"], "reference": "CmRSAAAAE1XdewawzG0uqKawfprYCictk4CWit0OEItnvlKVUSWXT33nUbn2XhGHDnh-m7pNleOs7TUuXGXdDCpCw6-FdfyVaZL4tQBDOzyPCSipqLwcmCSFdLRs_I1jYF6bbm0XEhDRD0zVe_Oc5vvyi1OQArA4GhQ18UqaHiMnzyuSx14T0HTHppF_0Q", "name": "Houston Audubon Society", "rating": 5, "id": "050a5458d86bdd1cee7b09678bd6256d0a20a73e", "job_title": "Ch2m", "place_id": "ChIJlQOxwVDbQIYR2uX_TZl0TYc", "address": "440 Wilchester Blvd, Houston, TX 77079, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.56820189999999, 29.770778], "type": "Point"}, "properties": {"photos": [{"width": 1800, "height": 1200, "html_attributions": ["<a href=\"https://maps.google.com/maps/contrib/108765250995932379967/photos\">Audubon Docent Guild</a>"], "photo_reference": "CoQBdwAAAKDWngUQwX-bcK-W6ISKGKSERt9K4_4oJfQXhuZgwpZQPbQuOHhOLtw_WxNQgWS5euXd5g6k9wqIvfMZHl6vch7W2QRDlt4h49sguyNjbwQLPIx2VYyHP8z37J8dZmiG4lPCbbihHNy2t2BJIetuUWyaOqdiondd57n9HmB5Hc_oEhBp9JxoNdh8WuHO1R9xMfTaGhQI9M1_4sPe3-qfUhlq2cLxrEH-Ww"}], "types": ["park", "point_of_interest", "establishment"], "reference": "CmRSAAAALxHm0Phqs7QepCSb6plkLl3_9q-bbKwm3Amyqbc8i32Q_N56y8Zn8CjrNMuCE0Y2dUJ4AD2pLTUa8-YKdx2EHioNE6r_KloUEyg95q3gfK_yb-IJCXaWewsuw3eYgCXyEhBoBci-l4-Rl5nxI2ITbUDlGhQDmqS4YEXyHt9gy4fNI_fKiiCIRQ", "name": "Audubon Docent Guild", "rating": 5, "id": "7ddd5daf76cc4979e2ba6b062322d1c77d5d1c07", "job_title": "Ch2m", "place_id": "ChIJI9XyNFHbQIYRtwHb8EtTpeU", "address": "440 Wilchester Blvd, Houston, TX 77079, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.44932349999999, 29.7803218], "type": "Point"}, "properties": {"photos": [], "types": ["point_of_interest", "establishment"], "reference": "CmRSAAAAJPcjYqu5otQDU8polmMT26x9PIXdj0Qo9diFpmU2fn-u0jq3g3rI2R9a3bri72KEtLWPiwielu6rJ-X9iMSi2i6-_p-uQeUN9SIC0T1E4P_VdtPz5_jySCcZfuLofcxNEhARPf8iAik5q5Qp6r5sxIGBGhQP_GCRSlv9ld7HlSg99y7W5TVa4A", "name": "Coastal Conservation Association-Tx", "rating": 3, "id": "7258b034e119f31e82320bca6e72781ee9f79d75", "job_title": "Action-Potential-Learning", "place_id": "ChIJcekacM_GQIYRPzL13cgQrPk", "address": "6919 Portwest Dr #100, Houston, TX 77024, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.47039, 29.655454], "type": "Point"}, "properties": {"photos": [{"width": 5312, "height": 2988, "html_attributions": ["<a href=\"https://maps.google.com/maps/contrib/101184977609161362375/photos\">aug4</a>"], "photo_reference": "CoQBdwAAALoWzsY_xPxzNAd8DMoIsVg3bf-F002PbnSNpT62Nl7VgKWQen-AbBInNnAvKUq-CG1iobNl0A2CjkOnZ5v9wlZu59dg_-F_TO8dYfBTmCYRvmCJdzf2bZ3zgJPMejua5ofCN2b9eMcxcf_qEQWdKlWYY9h-GeRHO7sc4CGJUZRFEhBT_5gCNh6Wox7s_ZYbEvDMGhSo1nRMiy6k6DR9UPrdL-fIiZPZ-A"}], "types": ["park", "point_of_interest", "establishment"], "reference": "CmRRAAAAwRjxouotoQrC-DgSlNq3oJPzIDUlT2J8gu0i8J4kdaNa4aoGVGjKOqVvTGbYI1UpuWDG5KjmojRJiQLum5PMoMePHVJHTIaAzQ1FAy_xQiOySDiF7BJiWrnBkJTQtdxVEhDMfX1HcxhWxuzLTcaeZV2BGhRwVA-soXvUlJzPIZ-F5iFyJ1CNKw", "name": "Willow Waterhole Greenspace", "rating": 4.3, "id": "0127506e8071350c2d48f0ca56e939045297a0f4", "job_title": "Action-Potential-Learning", "place_id": "ChIJR6_2zTzqQIYRsA7wExgfDWs", "address": "S Willow Dr, Houston, TX 77035, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.4003322, 29.7388505], "type": "Point"}, "properties": {"photos": [{"width": 1136, "height": 640, "html_attributions": ["<a href=\"https://maps.google.com/maps/contrib/117056878997299689379/photos\">Marisol Brown</a>"], "photo_reference": "CoQBdwAAAIi5IEL6NrxSzS-MenT2lwS6rdu8blLzF4Tj6kWW6fhO_4txJdgGpM8MBTu9YKD_qf8KqFWb70AX2QnnjZqL94-HQ-cfgOjk1BYYX_3A1W0MOWvROUxXWXOICWBKaffqWDGR4ugidz392abMgD6CxQkIXXGhH249pW9GlM44V5J2EhA2lH_eZ9-P-Suh4eqaR7T8GhRR37Bym0tNiC3_Xff4YRgJsTpleQ"}], "types": ["point_of_interest", "establishment"], "reference": "CmRRAAAAhMnzx25u5LPcAKbb_4TulOX8Tz13poZ64zHS353VNkG4o3Pc5GmDEWbo6QSlTy7xjBaHH9Pl9itVuBmcjEoK_21653R4gej0n4Q9xbEUVZsplcsH6W87DSo8d-4kbw7yEhDzKADXmxaiidyVbN7ZJBU5GhQl1XtheiDSDD_sTFOGpw6fXbBTkQ", "name": "Masters Fine Art Conservation", "rating": 5, "id": "a462c2eef4e22ea319485ae7b84f3d20756cbdd1", "job_title": "Action-Potential-Learning", "place_id": "ChIJp8u2bZvAQIYRbosnWz6cVmY", "address": "1612 W Alabama St, Houston, TX 77006, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.3876169, 29.794149], "type": "Point"}, "properties": {"photos": [], "types": ["art_gallery", "point_of_interest", "establishment"], "reference": "CmRRAAAAtMh9bcFfY-fGovS5O3B0OcL4jJ-Fq19IUdX7dUc7WbJd0f3ZU5zDHQH-wJVGaEsj7kLYk0v-34OGvsLXWYXNmoN__M3R3bmVdpAQBiMKUPDacO4AgI2QE13JGlsd8fB5EhAOymFClQRq8uuW3-MkDsF1GhSivXyb5u4TmLGDS7WPY6I168Kuwg", "name": "Whitten & Proctor Fine Art Conservation", "rating": "NA", "id": "883a8c5ef35ab28e1630235ad65a6b16506a67fa", "job_title": "Action-Potential-Learning", "place_id": "ChIJ8YuXE6K4QIYRn1SF1hazFEw", "address": "1236 Studewood St, Houston, TX 77008, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.3858767, 29.7300997], "type": "Point"}, "properties": {"photos": [], "types": ["point_of_interest", "establishment"], "reference": "CmRSAAAAxjoT9Re0HScoR76KGj25NAUdcgMnTFalzM36sDGs7I9lePaYGgi3a5yYKRJLkKZxBM73tQjEA9M7Tvv3nK3N48jA3oeRbrskjIRxCKaJ_RsC3W2KOybcl3XeBvoXvgVaEhBO2YZIpQls9O8z_eC2L3faGhRcDMG697tKAylH1CRV9KHZfNpPiQ", "name": "St Mark Fine Arts Conservation", "rating": 5, "id": "ea2d4bac6d74716b33f456dff3aae0cc0b43cca3", "job_title": "Action-Potential-Learning", "place_id": "ChIJKbDEoXm_QIYRcRFBlp0dE8A", "address": "4901 Main St, Houston, TX 77002, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.483218, 29.7482286], "type": "Point"}, "properties": {"photos": [], "types": ["point_of_interest", "establishment"], "reference": "CmRRAAAA9NfyI3pAbGU1Z-gmpkbqieCFhAV6_cRYv54IrLgJKg-LwaHWtEF2zBZWaYDeMHIHVhlCB1y057Gvkvhut9bC7B9yBSdlW8_qJTDmlvnT_v-iQDZq6LN4oi5hmJorLWzUEhCAkHUWaPkEDfwSSxFKfUpaGhSQZJQ5bqxGddjfhMgN6eHr566jmQ", "name": "The Nature Conservancy", "rating": "NA", "id": "90af6fb9fb926dde9f7103577cebc4150bbb1dec", "job_title": "Action-Potential-Learning", "place_id": "ChIJq-m4EX3AQIYRJkn4Lhccp2E", "address": "1800 Augusta Dr #240, Houston, TX 77057, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.42318089999999, 29.7345943], "type": "Point"}, "properties": {"photos": [{"width": 750, "height": 437, "html_attributions": ["<a href=\"https://maps.google.com/maps/contrib/106788706324997826205/photos\">Erika</a>"], "photo_reference": "CoQBdwAAAOd1AjatPcPzTjgAf_kO2ZPHrygyY8JGWO2iX4NcHYDhI1S0n-o-FVgtALPS6G4ZEwaMmHOVyW1FJIosTpA4rOXKVrFbfLCc3rOBlrVOLRXXUr7__nFdwT0V7saqkb3It9t7EpNK8OV03Dhu9ZI6OjObAME0KwpIvlQ-V8olysr7EhAtuXDTSSZS9dzDbyBpB6HIGhQdzdjqelNhmWLfV5GTyFWRVm1DgA"}], "types": ["point_of_interest", "establishment"], "reference": "CmRRAAAAWm8LY11rmtQzh66fG34Fc-3E01z1t8rRpXDPbrG4_ryXHVKRx0ND0a2A5rguepaIeKRZ8aFeaZPXd_vfKx_jxo_tMruUBr7A7Ay0vKd8nPiu28qrCwf6GU-zpjqfNdVLEhCtA55GpG8FiyergtyAUau7GhQyaepr3oAO_KEXEb6BHy5I_mY1fQ", "name": "Student Conservation Association", "rating": "NA", "id": "1c5ea7722fc0d99e9f7dfca55f5d9078224d51d3", "job_title": "Action-Potential-Learning", "place_id": "ChIJQcqBXfDAQIYRErawO-goGj4", "address": "2990 Richmond Ave Suite #400, Houston, TX 77098, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-96.038102, 30.055621], "type": "Point"}, "properties": {"photos": [{"width": 984, "height": 985, "html_attributions": ["<a href=\"https://maps.google.com/maps/contrib/110279808588468038448/photos\">Peckerwood Garden Conservation Foundation</a>"], "photo_reference": "CoQBdwAAAM2N9ltYHJVO87_QJ-xrxy9qzl13FaqH09azmlNZpvJnRikoqL0C8yndaUf5uAaX1pM3BCqt7-h86unDiTmZfq2qKwe0QGr2LY5DasTSBTm8VjCuEpjpmYoo9AweNZioFtPbUYeV2fRTFAsGl_swU3YZa216hyDmeuY5DbF871wxEhCZRKHUx_rfbfvOvEaAukd4GhTRkiII5oPRvKbeCsuDgduBVkqqzg"}], "types": ["park", "point_of_interest", "establishment"], "reference": "CmRRAAAA25BH_SJUUrj851UsAaLu_orcS56H7MV67AHJsLUw5WC3K_21vRdHwKyBJcitZgrMhpV4rMEX3XD1gLB0b1CCcuo4eFelZoRubhDULGyZKsT7Ri6qVp5JLfdmm2Cw45bjEhCEpG6qyVC1gPlyWpP9uBXvGhTtANdncwOeuzu_59kpEEqjV53bAg", "name": "Peckerwood Garden Conservation Foundation", "rating": "NA", "id": "e618a4c618cd67ce4f5fdc165f640220ab3b53b2", "job_title": "Action-Potential-Learning", "place_id": "ChIJmUR7pvHKRoYRIIl0o73bPGE", "address": "20559 Fm 359 Rd, Pine Island, TX 77445, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.64386449999999, 29.7515036], "type": "Point"}, "properties": {"photos": [], "types": ["point_of_interest", "establishment"], "reference": "CmRRAAAAHb2s6SJxUcc5_N8natdd6HV3svbTc8Je_XVv3-B9J6Typ6BZNDlfYqKwJVOGOa2xkmHIqhc5RZ-kNAcikJUb60fSk6tZ0HScgL04MAJRmeRRX50aneKifz2SwedK6yeGEhDRlJWNSuG_SGBZzzlM_YjDGhQqnu0t_aAkbXblrlGoXI6gBCpmeA", "name": "H2O Conservation Technology", "rating": "NA", "id": "30c07988ef8dfc62dac712b9d587daa4a36f2539", "job_title": "Action-Potential-Learning", "place_id": "ChIJIWZRKeHKQIYRXxta3wOMGGc", "address": "1725 Hwy 6, Houston, TX 77077, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.5705632, 29.7714443], "type": "Point"}, "properties": {"photos": [{"width": 3024, "height": 4032, "html_attributions": ["<a href=\"https://maps.google.com/maps/contrib/108143329814504597326/photos\">State from Jake farm</a>"], "photo_reference": "CoQBdwAAAM9w8Q4iJExQiC91qQxj-avdTsm7zVcB50hioh8pzuG1xwYqHzQA-9qEP9IunQw9Vnhs0zWqWsBouzyyo0KNDrzgRi2XowJiExGDcPsG8fyOHwMdam_JwFxaP0TEyTdHm_cQQj2meMtlDxROUOCR6fWsQoC7M0j6qk_1ZKNHcLqDEhCR0hfzYZegHBgyRx5SokqnGhRj7byezfZ37_cMVrXLBmJDo0exEw"}], "types": ["park", "point_of_interest", "establishment"], "reference": "CmRSAAAAAAd4BNKdSuJy_h2y8PJi_XUeDl5MWworGOi6QCH-7caHTITa5BWXacuCFOJfutL-HfIJyP6T2qs76EwTJDGSMKc7zNeqaYKM6HjK0AVXsc7uXIms8iFsu5aAP3Lz13o9EhAZ5q2MHCfH5Wlknbx0ax1QGhSOCjGau1tgFTRxh2YpfAwxnsYG7Q", "name": "Houston Audubon Society", "rating": 5, "id": "050a5458d86bdd1cee7b09678bd6256d0a20a73e", "job_title": "Action-Potential-Learning", "place_id": "ChIJlQOxwVDbQIYR2uX_TZl0TYc", "address": "440 Wilchester Blvd, Houston, TX 77079, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.56820189999999, 29.770778], "type": "Point"}, "properties": {"photos": [{"width": 1800, "height": 1200, "html_attributions": ["<a href=\"https://maps.google.com/maps/contrib/108765250995932379967/photos\">Audubon Docent Guild</a>"], "photo_reference": "CoQBdwAAANbLwAkMjiPzoTDS5tfH4tiRzRqAb5VPWvRNqj4HqS_c4IECjcNKDyS-_Vd5matFU7uBaaDst_F1lQU_CHHR8QDHVCl5Ku6tS1yy3WX93RI1DwGZ9sapoaZ5UWgdqj3LvP_UZQcBJ2qdMETAYbtIisfzGXByha5GnHh_5qQff6gsEhAi8jxghRkfnFy35p7NNnHaGhR4RghvtgKkIbFFqeBAxzGAF3I0fQ"}], "types": ["park", "point_of_interest", "establishment"], "reference": "CmRSAAAARqzRh5VpqjxYfHTzEZWjDuK05uKau5j-dn2SHzPAGeA11a-we63GM550RTELkH6xTUDf3Hj37obHdFln_YTiUvdNHkuZOhllYu0kw-WPnnLyk7bPR-tdtd1XOdJPf8kQEhB3cwOvz7Da5955y25AirRTGhSZxKKtbpSV6zC66qy6N_WsrjmI_A", "name": "Audubon Docent Guild", "rating": 5, "id": "7ddd5daf76cc4979e2ba6b062322d1c77d5d1c07", "job_title": "Action-Potential-Learning", "place_id": "ChIJI9XyNFHbQIYRtwHb8EtTpeU", "address": "440 Wilchester Blvd, Houston, TX 77079, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.44932349999999, 29.7803218], "type": "Point"}, "properties": {"photos": [], "types": ["point_of_interest", "establishment"], "reference": "CmRSAAAATGl9hIdTaZnLwP56FB6pVMVlKsS8yY4CK4gL1ihDu0T2poc4kCQX8sYN13J1x3lU46bt8M9AwmGMi8jbsrmjvQ9k4VwuZKdgaecLZvF_Rj2RbPHwJgwyxNcIrV4o5DyJEhBVLycc2bhBN9uo8p2tiEIWGhTbUAGD-YNCV94nOhQDmcMPESI8YA", "name": "Coastal Conservation Association-Tx", "rating": 3, "id": "7258b034e119f31e82320bca6e72781ee9f79d75", "job_title": "Mustang-Cat", "place_id": "ChIJcekacM_GQIYRPzL13cgQrPk", "address": "6919 Portwest Dr #100, Houston, TX 77024, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.47039, 29.655454], "type": "Point"}, "properties": {"photos": [{"width": 5312, "height": 2988, "html_attributions": ["<a href=\"https://maps.google.com/maps/contrib/101184977609161362375/photos\">aug4</a>"], "photo_reference": "CoQBdwAAAAr9xepo1l2d1C2cJw9bNnxcNmO6bzCFFeHzVLBPIJ605TgLhm5udBWt16H0rY0KVLFHZczv2HNMS2tmfrobzpD8iZaNOYlACZNN6_5C6Ls7f7IvXwRrpAt85gkHMOnX_e9YF4US2KfTISJRoaG-lcpYuLmyiHtbAZv6p1pXIZKTEhDcFfJzF_OsUQumntYRK5nqGhTejOjuHqIZ23hSp14GEJoIAhzvHg"}], "types": ["park", "point_of_interest", "establishment"], "reference": "CmRRAAAAvQ8K4x4UbSCjdJDBnye5T46n9-7_1U4um_jWK28M8FKxdHtwdCA--ab869TfLO1l1Y7yQNWaBuU7gmJ5Mq_WaK4Hf-M3jBl2rnUAjDhHk7xHFZ4zlInlvX7cpvoQhhIaEhD613iYBRlWETab1XkKXmhnGhRQlgkGjpkpZPzD9dyPrfZvDUE1QQ", "name": "Willow Waterhole Greenspace", "rating": 4.3, "id": "0127506e8071350c2d48f0ca56e939045297a0f4", "job_title": "Mustang-Cat", "place_id": "ChIJR6_2zTzqQIYRsA7wExgfDWs", "address": "S Willow Dr, Houston, TX 77035, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.4003322, 29.7388505], "type": "Point"}, "properties": {"photos": [{"width": 1136, "height": 640, "html_attributions": ["<a href=\"https://maps.google.com/maps/contrib/117056878997299689379/photos\">Marisol Brown</a>"], "photo_reference": "CoQBdwAAAKQN8mmScJNJD34j0YWCoRU2kEEwzi5pKJwfWGKU3DtvXvzDbO35CzAYvycxF74a4_yYub1E4yTqaIfTbtUdC8H_OPc4X11DqPAAQLzn17cWZjx4YetzUdC6TMS6IDynkqefTHOF_eJMZacBcVdbxIM2GCZ-ah7yRq3fPby2sX6hEhCo-pK-gq4FuX9cVysWyAhOGhRp_NGI8lWwFVYZaCLgcInB4BJ5sA"}], "types": ["point_of_interest", "establishment"], "reference": "CmRRAAAAl5-3U-exEF3rc85crryeJpWgY1mmmijx8IvUbRsMJlFcM9k_dvrgj0ehxpFDJOq9F7Zs5yEcN4ByotLkq1BZAGYorfv_VPAwJCcvhGIQH91BPDBJg9NZdB7PTzlBC4DBEhAAM1xeawiZS4ondpioJFJSGhRgrO8cjD10vENVuFsixe-I7dPHMg", "name": "Masters Fine Art Conservation", "rating": 5, "id": "a462c2eef4e22ea319485ae7b84f3d20756cbdd1", "job_title": "Mustang-Cat", "place_id": "ChIJp8u2bZvAQIYRbosnWz6cVmY", "address": "1612 W Alabama St, Houston, TX 77006, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.3876169, 29.794149], "type": "Point"}, "properties": {"photos": [], "types": ["art_gallery", "point_of_interest", "establishment"], "reference": "CmRRAAAAO9B_MmQ1dgmKWe1FDzh4vjBYuqgh3hmmUCP1tdpYPXKKL9VaOTuOumlkdimwILAkW4wjYHt4EFg41V0dKdsLt0E6XxTegjALxPWa6eMpDaBgqrZQcmc00Fy8bSWrjeWLEhDMLfg5J_9aUGJwD2xXmyGGGhRQ4NGxvFpFl5hxtYdwXqpF9U9URQ", "name": "Whitten & Proctor Fine Art Conservation", "rating": "NA", "id": "883a8c5ef35ab28e1630235ad65a6b16506a67fa", "job_title": "Mustang-Cat", "place_id": "ChIJ8YuXE6K4QIYRn1SF1hazFEw", "address": "1236 Studewood St, Houston, TX 77008, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.3858767, 29.7300997], "type": "Point"}, "properties": {"photos": [], "types": ["point_of_interest", "establishment"], "reference": "CmRSAAAAzN7KWZxI8t19ZzQjtbQ6aE8PKvm0Uu-j1rI9tqgmkJdulj_NiD0D9EqBXxGRHS9Q3mUATxWs3OkDCvclVMSeZDuZx9zLcQ3dk0tsgOroOhHmvO9JB1u_neIvVr6QCoQvEhCsJSzzJ00HdwJK0qW7OMohGhSLsH5qiF4hzx03R4I69CTiCSug2A", "name": "St Mark Fine Arts Conservation", "rating": 5, "id": "ea2d4bac6d74716b33f456dff3aae0cc0b43cca3", "job_title": "Mustang-Cat", "place_id": "ChIJKbDEoXm_QIYRcRFBlp0dE8A", "address": "4901 Main St, Houston, TX 77002, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.483218, 29.7482286], "type": "Point"}, "properties": {"photos": [], "types": ["point_of_interest", "establishment"], "reference": "CmRRAAAAywBI9XUCiVeLeU3nuT3KpuV1tfjETuPFa_G0No03fRGIX3qUEH2p08ZTbzz-wXxWAxqA3NHnTqFdU8zHG2imFYkRYiz4hrtnqh8MDhH9Z1An7pvYyEjL9BS5pKNMMJ87EhAHV2XYvTLQWrHB3asJRO_LGhT2JXOlIMIfjruyjQYhLrPOJRAc7Q", "name": "The Nature Conservancy", "rating": "NA", "id": "90af6fb9fb926dde9f7103577cebc4150bbb1dec", "job_title": "Mustang-Cat", "place_id": "ChIJq-m4EX3AQIYRJkn4Lhccp2E", "address": "1800 Augusta Dr #240, Houston, TX 77057, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.42318089999999, 29.7345943], "type": "Point"}, "properties": {"photos": [{"width": 750, "height": 437, "html_attributions": ["<a href=\"https://maps.google.com/maps/contrib/106788706324997826205/photos\">Erika</a>"], "photo_reference": "CoQBdwAAAInEmfINA5GKp9jM4S04b_zIVaR5A-CexzIuEjxTxEAU2bWychLi0CRukXFvHdDnYEUE69YCbNwdwRMpGb_y8FDhyHB1CGF0Ma6u_vigjkj_1IEfUzrZbqNYSDdjHmYWqGLuE_ePYl-a-CKXo5i297KDEssnvFIKLyg041m69ljeEhD3YuXVygTVahwmyBa5HYbCGhQcK-LiT9H1ZlNGczUuceV8CHo_lg"}], "types": ["point_of_interest", "establishment"], "reference": "CmRRAAAAKVWM-ZKxA0rb9IWj3EWONI1H8VlMzEBJLGGizxMyF3NM0SdIzWUkectltg-ET10exsZs6CZwm8UsO0AYbmC7loeTm3-LQr-fwkHfcCNnZeNfg1ye5T6Eo_k1D_rYs1uFEhCztCLggvS0YwgirY0v4uDZGhSc8-ynj8rsKNao8IpnNdwz5ZVUSQ", "name": "Student Conservation Association", "rating": "NA", "id": "1c5ea7722fc0d99e9f7dfca55f5d9078224d51d3", "job_title": "Mustang-Cat", "place_id": "ChIJQcqBXfDAQIYRErawO-goGj4", "address": "2990 Richmond Ave Suite #400, Houston, TX 77098, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-96.038102, 30.055621], "type": "Point"}, "properties": {"photos": [{"width": 984, "height": 985, "html_attributions": ["<a href=\"https://maps.google.com/maps/contrib/110279808588468038448/photos\">Peckerwood Garden Conservation Foundation</a>"], "photo_reference": "CoQBdwAAAPn8U7juKmx1TOTxBnMHbti9BDymdOGTEZlkQ0-epg_p8PzCq77l9hlf2BqqZ12d0UBz3bSpxDL3i6p3wx9zZVaazqomz5lN8j3odMdb1CMaNXvSGLw8o28JbZlxvxN-1ryYucOl8Vvx_fMKTTdn_oGJrtWvTIttu4KD1LBgTONAEhC6Cq3u_KYLvuLC2JIDy8HbGhR0P5ApGovRQh2re73CmylbdRXkZQ"}], "types": ["park", "point_of_interest", "establishment"], "reference": "CmRRAAAAb5QV2yySf_K-khB44QsYf_Ba2vEZ-lbInODGuyuI2Cpekxexv7CqlLGNQj9QDEdvTVarFBTEQq-jU2KfL0FA3LilxmRm3Y8dKLp7Nav_SHOw9pZNwfE7WWvYKk6-HSlSEhD7T6hZGpnzulEULIElYJ1dGhSIrTKDYdFEFm2EMfq8xcNsN8ylGQ", "name": "Peckerwood Garden Conservation Foundation", "rating": "NA", "id": "e618a4c618cd67ce4f5fdc165f640220ab3b53b2", "job_title": "Mustang-Cat", "place_id": "ChIJmUR7pvHKRoYRIIl0o73bPGE", "address": "20559 Fm 359 Rd, Pine Island, TX 77445, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.64386449999999, 29.7515036], "type": "Point"}, "properties": {"photos": [], "types": ["point_of_interest", "establishment"], "reference": "CmRRAAAAmf2ul-ZluEg-VNg1cMWJEnCUn1fiDPVIoDWhxVWT9RFtGj-qof2uHe9V_iqbkwegrtqfknlorshpOAJAd9LLI9dPWIUuq2O4kN0KX3kpTHPzM4e5NVhmI2jBAF0J1zXgEhBweXlBffW4E6SO0mZFSCAaGhRT-TXYeNG_mbAG0WPRo9fG9DcAvQ", "name": "H2O Conservation Technology", "rating": "NA", "id": "30c07988ef8dfc62dac712b9d587daa4a36f2539", "job_title": "Mustang-Cat", "place_id": "ChIJIWZRKeHKQIYRXxta3wOMGGc", "address": "1725 Hwy 6, Houston, TX 77077, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.5705632, 29.7714443], "type": "Point"}, "properties": {"photos": [{"width": 3024, "height": 4032, "html_attributions": ["<a href=\"https://maps.google.com/maps/contrib/108143329814504597326/photos\">State from Jake farm</a>"], "photo_reference": "CoQBdwAAADw_xbRKjECh5sA9AMe-igYMvsrnNgTn0595RTN1zCT3SA1v5VyUqIkSMuEeEBEgTs8TumlngWn5VZ8D1lZ2MtqMyrCfG-sSnsGCpU_9DPyNcXmqtNFUgb8XGyA-Zksm-EqDgBSuqzJbi2UzF7onErjR5u_hYxojGv2Dx8G3bAPNEhAruwt-WpyUI8YMVr7vkmJ1GhQUJBgiy4a7eBBIUuxrVnacSDDUQw"}], "types": ["park", "point_of_interest", "establishment"], "reference": "CmRSAAAAewDuQ7gud_A-Mj9EfriL1UbzyuWcExD0-ZvVtpKneN2gKChgshmniPtv1og7OAKK3_PA8FbWGK6_Espi-neJR3lK4CLE76COJgvLnEyPSykBbzkZzb8e2bewVtgKMdVeEhCiGonEa2C_4wSEy7S95nwxGhTOQnmOA2rl9c0bKE7RBbnRVUqHxQ", "name": "Houston Audubon Society", "rating": 5, "id": "050a5458d86bdd1cee7b09678bd6256d0a20a73e", "job_title": "Mustang-Cat", "place_id": "ChIJlQOxwVDbQIYR2uX_TZl0TYc", "address": "440 Wilchester Blvd, Houston, TX 77079, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.56820189999999, 29.770778], "type": "Point"}, "properties": {"photos": [{"width": 1800, "height": 1200, "html_attributions": ["<a href=\"https://maps.google.com/maps/contrib/108765250995932379967/photos\">Audubon Docent Guild</a>"], "photo_reference": "CoQBdwAAAHljmYEIX2kLVHfgoNae3u9HFEDtnYMThsMWIlrLxl-Rg8HnU0hK_PY43xMJEVNKAesnRzNvVoIp7_sx3-WPpH4Jn3L_obtyKtXiqVIos8clVmMq7iLR8hgA7hiitKuvON9GUeYZCqCh_DO3mUmOD59B0d0PYqfPAmShB6u_UiNMEhCpNR6tl5dhRklbo_KiApeCGhQ5wQ_kZ2UmPL5BLbUAGL6hZ_MMNg"}], "types": ["park", "point_of_interest", "establishment"], "reference": "CmRSAAAAKqWiKzZK_byJKgf0o5eU_kGugMkTOrRl0Pt4PGy22KYRJUaiMQXvhv4W0wPUUVX8C58Xvq-tXjLQkqmlGD1rV5Hh55R-pQ6rXLCr85v-eHTR8NNfcA93LeOYqskt1ZbzEhBj4mild5eiIglx_0sa1UkzGhQRUiLRfTRd24QkFRECRXk0ddfZOA", "name": "Audubon Docent Guild", "rating": 5, "id": "7ddd5daf76cc4979e2ba6b062322d1c77d5d1c07", "job_title": "Mustang-Cat", "place_id": "ChIJI9XyNFHbQIYRtwHb8EtTpeU", "address": "440 Wilchester Blvd, Houston, TX 77079, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.44932349999999, 29.7803218], "type": "Point"}, "properties": {"photos": [], "types": ["point_of_interest", "establishment"], "reference": "CmRSAAAAbbPtGNl0ty8eWYr4IdBqgTVLnZPKdkcJ1iNCRNN1PGmdv_0l6FD4klFaXBhPdADZSOhNiFYLP2UB0ubtvCgg3ShJG6-5zb5zQLsdj-fh8WZOuWG7e8F28krVBR7jW_AiEhCyVhyZgDebOH1WAe98MZuQGhRJ1_F6QSMM-fNjzE5uagQY1oHIrQ", "name": "Coastal Conservation Association-Tx", "rating": 3, "id": "7258b034e119f31e82320bca6e72781ee9f79d75", "job_title": "Ghd", "place_id": "ChIJcekacM_GQIYRPzL13cgQrPk", "address": "6919 Portwest Dr #100, Houston, TX 77024, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.47039, 29.655454], "type": "Point"}, "properties": {"photos": [{"width": 5312, "height": 2988, "html_attributions": ["<a href=\"https://maps.google.com/maps/contrib/101184977609161362375/photos\">aug4</a>"], "photo_reference": "CoQBdwAAALiT2FokVzodkNykMcHW0VmYk4j--fDiR1rth_3yVJjzta5GcvnocROgoYU0CuOgQr_4OWnae0YCUb7six0QW0OKsWsVYZdNOEddsZyycQifj2zAG3Cz8E17ECQCrVQFXkwAxnKQzBiQtQfbMWsA5xh5ulPz-I65s9Y0qzxYSjV5EhBe80zk6n2okohfYlSoOYOnGhSG6hkKaXSIkO2cQ_Nfeqherh3_Mw"}], "types": ["park", "point_of_interest", "establishment"], "reference": "CmRRAAAA4XHRCFSff9G234wjpCCiQohGrasMml8e_fw1LgIBXVzyxH29tPigivLjNd--XNuR2qwpVp9pLDmE9m3ycp-CvqmnfycAehn9dljw-71_ZvenGyyiRAuUAcD0CUCqsjSiEhDgQiLODFz3qSZYg9grMs-TGhQGtpyiZ8rvv3wsYdTMIh-t5DKX2w", "name": "Willow Waterhole Greenspace", "rating": 4.3, "id": "0127506e8071350c2d48f0ca56e939045297a0f4", "job_title": "Ghd", "place_id": "ChIJR6_2zTzqQIYRsA7wExgfDWs", "address": "S Willow Dr, Houston, TX 77035, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.4003322, 29.7388505], "type": "Point"}, "properties": {"photos": [{"width": 1136, "height": 640, "html_attributions": ["<a href=\"https://maps.google.com/maps/contrib/117056878997299689379/photos\">Marisol Brown</a>"], "photo_reference": "CoQBdwAAAA1cCL-sPM_q-BzjatQ0buQCDZJohYEAs96iqUZoNpozaJeqdFUkxDAnKNgy5ba7Bbyymc7vh0fuVnQ9Ye9bkQ3ZbC0qWRVlutstNEgAFa4MssLHiPbo3hxi749yIJkVI6c_6M5C-tva3awvolSZPCAswB3z_n450W0jA3xjh2DAEhDQsPdeWmDv0J6d1DbqNyMvGhSJB-oIfDuQI7Dy7ibz42H1CLS-zA"}], "types": ["point_of_interest", "establishment"], "reference": "CmRRAAAA8WGDuF4Hjko9qO5befhsiAse66uWEv2SiSbyVpNNL_JQnCRPsBNFA_qHCHZ484lbAv5MoFjJy7dccQoGNRnFdL47Ov4SaFBWtgB3RhnhVuKy83TaMiDp47zyliV_xwvpEhAuxce6SOj-0MpWpGSW3vxjGhT00uSmV0eR28o-Kq4ZiQhfqcJ2eA", "name": "Masters Fine Art Conservation", "rating": 5, "id": "a462c2eef4e22ea319485ae7b84f3d20756cbdd1", "job_title": "Ghd", "place_id": "ChIJp8u2bZvAQIYRbosnWz6cVmY", "address": "1612 W Alabama St, Houston, TX 77006, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.3876169, 29.794149], "type": "Point"}, "properties": {"photos": [], "types": ["art_gallery", "point_of_interest", "establishment"], "reference": "CmRRAAAA6varrgM3_KYUs1yvQVrQD_BIqPP-G9k-Y3V5UtyMJjsd249px_lINmDXZXKiyXhAJf7069ofp9bvJGEyLb9M3X2yJBK4SOWzk_Cma_saaqOjMzFQfaVPYdBnkRM0FAjlEhA79CKm6agomnMu14_Y2RGEGhQ_myVTBwf39KKtxybRUaOVPFHU8A", "name": "Whitten & Proctor Fine Art Conservation", "rating": "NA", "id": "883a8c5ef35ab28e1630235ad65a6b16506a67fa", "job_title": "Ghd", "place_id": "ChIJ8YuXE6K4QIYRn1SF1hazFEw", "address": "1236 Studewood St, Houston, TX 77008, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.3858767, 29.7300997], "type": "Point"}, "properties": {"photos": [], "types": ["point_of_interest", "establishment"], "reference": "CmRSAAAAH78LODoAA62L9_cahbdCmrC7eyAFaVyvqb3F6LgObGPrnXCW0YUYCVqb59-CP8H10oE04WBG1y_Pf4Jyjr7HpPRIyH9Vz-b9q0ie2Awllt1JmWLEGsXWUbGqbNeiMJZhEhDuRuMhrr37UfCzLsYk0263GhQvh5Qs7uDhZc_XqZfKCFoK0X0qMQ", "name": "St Mark Fine Arts Conservation", "rating": 5, "id": "ea2d4bac6d74716b33f456dff3aae0cc0b43cca3", "job_title": "Ghd", "place_id": "ChIJKbDEoXm_QIYRcRFBlp0dE8A", "address": "4901 Main St, Houston, TX 77002, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.483218, 29.7482286], "type": "Point"}, "properties": {"photos": [], "types": ["point_of_interest", "establishment"], "reference": "CmRRAAAAL09nXi9Klbi30yzwqlVNFECN8jjBwcTqQ1RfvuKl3Oi1EDNo0GTK-fo-qhwEHQQPRIuOxVcytbypumv-Aai4i0fLk4CZchCDJkFdjsPKrZ9EzHeL7F6n0VUIvfNxOTDCEhAbjxWSJKoOUUaPn9OP0V1iGhRqlkYuXoFDenC9tWP9GzPPDM4Seg", "name": "The Nature Conservancy", "rating": "NA", "id": "90af6fb9fb926dde9f7103577cebc4150bbb1dec", "job_title": "Ghd", "place_id": "ChIJq-m4EX3AQIYRJkn4Lhccp2E", "address": "1800 Augusta Dr #240, Houston, TX 77057, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.42318089999999, 29.7345943], "type": "Point"}, "properties": {"photos": [{"width": 750, "height": 437, "html_attributions": ["<a href=\"https://maps.google.com/maps/contrib/106788706324997826205/photos\">Erika</a>"], "photo_reference": "CoQBdwAAABDDzW5h63hEECHv6yRq2kIpr_4st4-Mm_6zMlCXbcon4Zk7VLRFnw0OFrWAKoD4uQc-ZRWEAyO3ZSF2xUmPgcmhU9JsvKE2SR4_ApVf7W63YJz7eZHMh01-7X80LMEoc2nfdgwMPra1MuN1b-gUYVwVMNhNfZ_nyhxH4F3pQ4vbEhA0KOWJo9nnvG3QivC-sNTEGhSRQK6R4VYUpxUfqLSKG2qOcV7K9g"}], "types": ["point_of_interest", "establishment"], "reference": "CmRRAAAAFoYe7hs_Z2frSxPNKyDyMfsOQZHTDSv-wyClHiiB8uxSCFJUyMcjzPWEkEIyIxw4K75YnwTl57h1AcleHxj9zfsFgjtuOPeK-rwPXMLi0aw7natUns0MKEP9-LsZxbu3EhCIvBYT9sghXnR2JdnTi56WGhS0y3j173DyxTnn9Gipu75r7rBOaA", "name": "Student Conservation Association", "rating": "NA", "id": "1c5ea7722fc0d99e9f7dfca55f5d9078224d51d3", "job_title": "Ghd", "place_id": "ChIJQcqBXfDAQIYRErawO-goGj4", "address": "2990 Richmond Ave Suite #400, Houston, TX 77098, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-96.038102, 30.055621], "type": "Point"}, "properties": {"photos": [{"width": 984, "height": 985, "html_attributions": ["<a href=\"https://maps.google.com/maps/contrib/110279808588468038448/photos\">Peckerwood Garden Conservation Foundation</a>"], "photo_reference": "CoQBdwAAADuWzz3QlnW_HKBudJGQOQPtgcySA4FdlH7ICx2eYgjk7d6BljROJCeecgLHLxn8B85kXJsb7mkNRbxr3PySb0vQzTiZMu2zwq7U498UGKgEIW2xLrkdbcW1HCtbozO50Yf04YtXyUjfAslHbXgT_nFGTtRW6OsWA9xCw52t9CO8EhDsaUiK8BX3cbRCu1DGPX_XGhT26AEPD27VgARGDg30Gh1BHuUOpQ"}], "types": ["park", "point_of_interest", "establishment"], "reference": "CmRRAAAA2InJzrX-qt9TqY-zSIts2VyYBDvwFR9FwsKRGXQ7vBAsy6lcLPMqtagYzEeVMxmo2NeQpZKit0UYho2vBFK7LnFjax8F_Bt8wVpI0SneVT3U7M5hx4_V9-0aHRHGS-VcEhBuEMqKjpEVgN33jaOiGnzmGhTqW-mSJOV-wfoOoAJxZzyrFAuVAw", "name": "Peckerwood Garden Conservation Foundation", "rating": "NA", "id": "e618a4c618cd67ce4f5fdc165f640220ab3b53b2", "job_title": "Ghd", "place_id": "ChIJmUR7pvHKRoYRIIl0o73bPGE", "address": "20559 Fm 359 Rd, Pine Island, TX 77445, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.64386449999999, 29.7515036], "type": "Point"}, "properties": {"photos": [], "types": ["point_of_interest", "establishment"], "reference": "CmRRAAAAnA_UZIg1vJxB1MxFLX0ewEphESpT3yiUuom2ac8BoExn8GJZquF8Mkv4Ln7qcY6DQgVc_gANzc5eKMvc7mPJ3c3liw4hmfRybVqp1T_TwUDwliu1Rca4mx0DWvBRC6bYEhDIRIqB4huVePz7aRLKLEZ-GhSQFwjJqNl5GzY1nwtMC1N56mKHyA", "name": "H2O Conservation Technology", "rating": "NA", "id": "30c07988ef8dfc62dac712b9d587daa4a36f2539", "job_title": "Ghd", "place_id": "ChIJIWZRKeHKQIYRXxta3wOMGGc", "address": "1725 Hwy 6, Houston, TX 77077, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.5705632, 29.7714443], "type": "Point"}, "properties": {"photos": [{"width": 3024, "height": 4032, "html_attributions": ["<a href=\"https://maps.google.com/maps/contrib/108143329814504597326/photos\">State from Jake farm</a>"], "photo_reference": "CoQBdwAAADc70JOqpfAekhXeoRzbNnVArTXIOV14jMXj-2OeK-VqfTSydJWx99hAyUvK34OzjEwYVf05gpFn9kKeIA6BuzxqiI0eM6K0o24y3FUQwKxqp2n14xavG3KdwsjqIdoTqFWItCJk_tAhIsohIpOl9ZwzEIBM7ql_qF4b7Bt2w8RHEhBxen6IK8u3N_Te8P9Moxd8GhQJ-imIgFO6zb91vYnsRBzwT2z1ew"}], "types": ["park", "point_of_interest", "establishment"], "reference": "CmRSAAAAbN4wJhuAdGSafMP10x9XjuhJMYa2lxENC4JJITVWE_m-P3tnQydsfuLVePaFJF6CSOUHNkDM-WwwYDDBR6JkINuvpHnwRSg16uyjoqaXishnU2NsAJc1ykzlebiY1_FREhAMrn-PyN3e90dTvbYsiwQCGhS8hDdrziiRkCTo6iI2M_W5Ncx5Ig", "name": "Houston Audubon Society", "rating": 5, "id": "050a5458d86bdd1cee7b09678bd6256d0a20a73e", "job_title": "Ghd", "place_id": "ChIJlQOxwVDbQIYR2uX_TZl0TYc", "address": "440 Wilchester Blvd, Houston, TX 77079, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.56820189999999, 29.770778], "type": "Point"}, "properties": {"photos": [{"width": 1800, "height": 1200, "html_attributions": ["<a href=\"https://maps.google.com/maps/contrib/108765250995932379967/photos\">Audubon Docent Guild</a>"], "photo_reference": "CoQBdwAAAP7sPvNoBqSczcGqcDsRZngl6gQ-KzYycakJHpdqmbZg21PhaU22212SLcAQeCt5CUFdNpgwNXQJdL-UV80104H2F7ET0_onIlFTRncFCrsAqdB6fHrBZAjft10RVJFalDcTv0Uto7hv-MpSZKtMZZZbWBXOcAiYZryA6KI0aOCREhCtCHDSjvH1zXRPDxgMu2MEGhRxhM0ZtC-CeduZRaoJldPeI0mY-Q"}], "types": ["park", "point_of_interest", "establishment"], "reference": "CmRSAAAAXaY5WH9z3Ircn1UsTy3n_B8EU8KtOHchzpmQSYBuX_yIZOW47e9j8kVG5TXwQzjbtqws0HrXJ_8dFpHkRIb9njoeoksBwz7bPSeA8ogBoGPhfrcUR1QACijBL71s2kS5EhDJoWZFwP8-QxTg3LuSsizAGhTF9qgYDO7s6wbcV09MMRT3prkXpw", "name": "Audubon Docent Guild", "rating": 5, "id": "7ddd5daf76cc4979e2ba6b062322d1c77d5d1c07", "job_title": "Ghd", "place_id": "ChIJI9XyNFHbQIYRtwHb8EtTpeU", "address": "440 Wilchester Blvd, Houston, TX 77079, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.44932349999999, 29.7803218], "type": "Point"}, "properties": {"photos": [], "types": ["point_of_interest", "establishment"], "reference": "CmRSAAAASkiq_O4_v3N4zPNuzpFK-3bETV4ti5InRWf6bix_3Vzfgu3jKQHA0JXkul8TMY2XXHORgmTp_A218xw4Oy83J_k0SXuL_2mpTutLQ0l5uZ-zifX_6LCRGh_-Ct5Cw-l2EhBFIpSX4K9gFz4QpUvQKDX4GhTPQGJPyvmVDBZ-WBPBM9IBS763JA", "name": "Coastal Conservation Association-Tx", "rating": 3, "id": "7258b034e119f31e82320bca6e72781ee9f79d75", "job_title": "Databank", "place_id": "ChIJcekacM_GQIYRPzL13cgQrPk", "address": "6919 Portwest Dr #100, Houston, TX 77024, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.47039, 29.655454], "type": "Point"}, "properties": {"photos": [{"width": 5312, "height": 2988, "html_attributions": ["<a href=\"https://maps.google.com/maps/contrib/101184977609161362375/photos\">aug4</a>"], "photo_reference": "CoQBdwAAAMiNpfsKkY1iB3G7TQQ24Ans3mdUwt8T9tRayWHHtpLwyTUSJMXlpLr4en8SHXkDquR2qhEVE_er-LLnNBWF87cHtOlprq7PlbyQnIVpxNt9zDMTdMkCppm4gdVWt8X2D2y_Bg7gWNhJJDGqsNUnpsTxWJhPPlJ4eJbqbcJnWvCNEhCEBOpHThoRScdRe1KoZzi1GhQkcCYTuJGbnQXDXHsnVi0L6q5BIA"}], "types": ["park", "point_of_interest", "establishment"], "reference": "CmRRAAAAs15GqkG9kmtTbiDH6dAtWXx7tbOT9EgQwcF2EbyJacrZOQDMbakZeQQR9s1mRN-xp8iq_pLrFTE44TT1qMWjBqZPa1-liZRRTz3KJXobPDU7EEOwBRrFB7K83wGFIaXhEhDceAAStonHAlqq_27mJpkEGhTeMIWmQfvYSSLxQMUQePpVbhhDRA", "name": "Willow Waterhole Greenspace", "rating": 4.3, "id": "0127506e8071350c2d48f0ca56e939045297a0f4", "job_title": "Databank", "place_id": "ChIJR6_2zTzqQIYRsA7wExgfDWs", "address": "S Willow Dr, Houston, TX 77035, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.4003322, 29.7388505], "type": "Point"}, "properties": {"photos": [{"width": 1136, "height": 640, "html_attributions": ["<a href=\"https://maps.google.com/maps/contrib/117056878997299689379/photos\">Marisol Brown</a>"], "photo_reference": "CoQBdwAAABpB0t3jvdw2gKNVwdKdu05yNptiW08x57cA7wmVGNb-qZMrZK-nNQUwtbrBFI3XAVbYWCFB2eWs2owxZ67F9ZQoKc1IaVYAKSbFntm4Hhd-3m1d_PRL_f0uVY4GuXhlunUMc2OFCwNqryaulM9YcD5Ybk-DcUddwSU6wG_6w9qaEhBXZ4upavkL_FWqpSjv0g-8GhTDqnm6ZQ_RQEl35knCvhq5z19IOw"}], "types": ["point_of_interest", "establishment"], "reference": "CmRRAAAA14OZI4BqMX2m-qntMDxmpHYTAD2N87uXSz9CNE-AAKvz0ujBFbm2vwhTkqoZ4vv0lwwMBCUM29AtSZcnTGN__w_8s0_DcAuoJDBaJn4jPWBhllQETX6z9VOmzsiUqIgCEhDD2PV7Wlg5MyrjVulrUUkeGhQ63eBi0mQQpDFsd-Kh5UofLhYZhw", "name": "Masters Fine Art Conservation", "rating": 5, "id": "a462c2eef4e22ea319485ae7b84f3d20756cbdd1", "job_title": "Databank", "place_id": "ChIJp8u2bZvAQIYRbosnWz6cVmY", "address": "1612 W Alabama St, Houston, TX 77006, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.3876169, 29.794149], "type": "Point"}, "properties": {"photos": [], "types": ["art_gallery", "point_of_interest", "establishment"], "reference": "CmRRAAAAlQJ3Sc_2qgyc9sLSm2JAQft-bYu5Nl2WJT3M3liWYH7BsqqQOqd5I2WoUC9AXW4SErFjJC2knnfokIqmyqR6fWOtACGtukSQF5-Bs4GRCQQdlPjiu86lLlpQ1x44t-RMEhAYPPkq6KprIA8ZTj_1SrQ4GhT4aPXk83T53-X7ae_lHKr7iYMNIQ", "name": "Whitten & Proctor Fine Art Conservation", "rating": "NA", "id": "883a8c5ef35ab28e1630235ad65a6b16506a67fa", "job_title": "Databank", "place_id": "ChIJ8YuXE6K4QIYRn1SF1hazFEw", "address": "1236 Studewood St, Houston, TX 77008, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.3858767, 29.7300997], "type": "Point"}, "properties": {"photos": [], "types": ["point_of_interest", "establishment"], "reference": "CmRSAAAAc9oHa0LlOwKW-LM94nj777qdvrkGxzhAyxDp1J5fTf76_SR9aaQk81tuFR_iCxRXqr1AtJJj-tmlktgtJN09e3XfnWaczRC50untIbYiM9ia9iVKfi4LHzgCICWr0O_qEhDVdsuIHVi25agZH-lYJkxfGhR0BgWkIja5gtkEdkbh08bioVJowA", "name": "St Mark Fine Arts Conservation", "rating": 5, "id": "ea2d4bac6d74716b33f456dff3aae0cc0b43cca3", "job_title": "Databank", "place_id": "ChIJKbDEoXm_QIYRcRFBlp0dE8A", "address": "4901 Main St, Houston, TX 77002, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.483218, 29.7482286], "type": "Point"}, "properties": {"photos": [], "types": ["point_of_interest", "establishment"], "reference": "CmRRAAAAscJeW-j8Q821wXUHS74ZggR8qOdhUQmrKF7O6cRtWnDwiniia3xIMavUQlOWfaOMI2-btsJ6BNxlkB5SCLQWYEp88ziYGL3YgPvfL95Zcenp_JvTFUNddKoku-iOv4unEhAvbwTqHTk-W_wuw0PculFGGhRR1Si_EypU2sGJyM3GwmjHzRaz3w", "name": "The Nature Conservancy", "rating": "NA", "id": "90af6fb9fb926dde9f7103577cebc4150bbb1dec", "job_title": "Databank", "place_id": "ChIJq-m4EX3AQIYRJkn4Lhccp2E", "address": "1800 Augusta Dr #240, Houston, TX 77057, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.42318089999999, 29.7345943], "type": "Point"}, "properties": {"photos": [{"width": 750, "height": 437, "html_attributions": ["<a href=\"https://maps.google.com/maps/contrib/106788706324997826205/photos\">Erika</a>"], "photo_reference": "CoQBdwAAAD4VITijCY-HpDyN33lXZIzTNfvo9wMiEsKPLAZUwtQFwscwhcAWU0fpd9AT5XH-Y0Swtx60YcU6a_6jGvR2U6TAgRWL8td0yoNK1RJNXskYHel7imxqPXdLtyACQNf9d8QGi--QkbUPj-uaLm81Jn3VDEX3MWEsBzsXFMBzm1LeEhBO_bzfQn6zHdjGH8l796yaGhQvxhbJOV5Qh5j4pA0RYrYHT6qAqg"}], "types": ["point_of_interest", "establishment"], "reference": "CmRRAAAAZPFpf2-4qbkDaU_OJARzluLL1Kmg1OSo1C3qpE4K84eoz97pBIBOqrHZ2_H6_i5icJBer3YE8hs9QbEVBw-l73UUCVtkSmzcyXWFhh6HW3yCCsLbKowUJVjZVit3pr-uEhCipdPrK1wY_3_2ZeR72YHPGhSVdjcFtWz6Os0Pa53chpxHO4JZuA", "name": "Student Conservation Association", "rating": "NA", "id": "1c5ea7722fc0d99e9f7dfca55f5d9078224d51d3", "job_title": "Databank", "place_id": "ChIJQcqBXfDAQIYRErawO-goGj4", "address": "2990 Richmond Ave Suite #400, Houston, TX 77098, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-96.038102, 30.055621], "type": "Point"}, "properties": {"photos": [{"width": 984, "height": 985, "html_attributions": ["<a href=\"https://maps.google.com/maps/contrib/110279808588468038448/photos\">Peckerwood Garden Conservation Foundation</a>"], "photo_reference": "CoQBdwAAAI8XgCfiwypTIKF7Vc_FH_R-4CF-vAalBDNhTWlXCIhbUCAv9fatRj9jDbameVYJQRyEFQxs68TAYvAQmOExXzaPSE13-6SsMNgcMWluqSX-8AY68Ngt2KGf5USYxr4iVMpBs-guU4xNzFd6NqPluFLXQwfFax9x0W3T50NVabUgEhDEnhXfQYZUl6IBGkTZ2O6XGhSNEEsOWYRTkGMHMf2hvO7tVjW7KA"}], "types": ["park", "point_of_interest", "establishment"], "reference": "CmRRAAAA8F9Ejv5nCLWkmfbc_NCDi6CPFn2kZtC88tYAJ7XxIoQzgSGlD7rSnBO6Kh9DNuyK8vLUqLNJLFkLI_4ytuspMQ0fYKM2HtxpLsgQjjwyNnk2SW-Sp8PGrdHSklmIV3JdEhB26AcMDp4KhlXUg1S1HBlcGhSO88h58gPb_P_IpeSqhKUO4OhGTw", "name": "Peckerwood Garden Conservation Foundation", "rating": "NA", "id": "e618a4c618cd67ce4f5fdc165f640220ab3b53b2", "job_title": "Databank", "place_id": "ChIJmUR7pvHKRoYRIIl0o73bPGE", "address": "20559 Fm 359 Rd, Pine Island, TX 77445, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.64386449999999, 29.7515036], "type": "Point"}, "properties": {"photos": [], "types": ["point_of_interest", "establishment"], "reference": "CmRRAAAAqpkI2oiME-6cz7puVTLFoIpBIgRQA4T-hnnCtf2P8o7CpKpQe7VNhyrdvsC5zwIa6YLLeMNKlJVT37J0Jqd8h_pVGEI8cGbKwCs55xmdF3sp0pzFX1SGTjXZhxauvSoUEhBrUc_C2LV_FVLPW1KEAWXEGhQ4H_IrwQ0-4jwyFc49Z6rHWa-Lag", "name": "H2O Conservation Technology", "rating": "NA", "id": "30c07988ef8dfc62dac712b9d587daa4a36f2539", "job_title": "Databank", "place_id": "ChIJIWZRKeHKQIYRXxta3wOMGGc", "address": "1725 Hwy 6, Houston, TX 77077, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.5705632, 29.7714443], "type": "Point"}, "properties": {"photos": [{"width": 3024, "height": 4032, "html_attributions": ["<a href=\"https://maps.google.com/maps/contrib/108143329814504597326/photos\">State from Jake farm</a>"], "photo_reference": "CoQBdwAAAJmiCJcSQdykWLBJGWy1N49jFjGMkNW81rEGENl89UwIKDt5INxUcYifIXsBwDJAl7F6DSoX0pZ3qHVP45XR6vVAKVsMuK-1yhBuB-xjp-IiSm6CCbiD4vtlHEhDyhoJWfP8NNWwgfLK8lFM0jdIxB43_GZ1wQ4uUQA7bUdv_dROEhA2Ue742CQNwquIsya_TytOGhRdpPV-Z_3ps8kdluLD5bfhyqmrhQ"}], "types": ["park", "point_of_interest", "establishment"], "reference": "CmRSAAAA_THyJ4Tl67LqV_0kxqnAb4DUP-NRrSP9Q9mbvqJSzO6Vh13GMpdh5_zHBEpZk8cPsDRydCYTX5aGVl8A9w9TM9gPaXJZEiSHrfl66gsbLiut-YJOHUN6Abvd_w3kBA5uEhCIqFqNKHyNRQxc2kaw6FldGhSAU4rxsMHmk8P1ZNbC0_2WKNT6yw", "name": "Houston Audubon Society", "rating": 5, "id": "050a5458d86bdd1cee7b09678bd6256d0a20a73e", "job_title": "Databank", "place_id": "ChIJlQOxwVDbQIYR2uX_TZl0TYc", "address": "440 Wilchester Blvd, Houston, TX 77079, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.56820189999999, 29.770778], "type": "Point"}, "properties": {"photos": [{"width": 1800, "height": 1200, "html_attributions": ["<a href=\"https://maps.google.com/maps/contrib/108765250995932379967/photos\">Audubon Docent Guild</a>"], "photo_reference": "CoQBdwAAAAKhOtSt34Wc7qJdjtoWX0qqG2dJbEWt2h4vQcjuldtVl33OIcFWqhlAF3cqdIggxs2u3zOz8XX1-zCXfN_UwN667VasMyinWjSrI6D5jAQnn8W0yepjojDZpXe2oeA1F2YDlW31l0dWXdyNrPwFaQjjowkbScUvjF_43Yvn3xWMEhDD9wPP9nxTpNOSuNN9aaU_GhRWJ72F86cyqRgerXNVuK1x_SDb1A"}], "types": ["park", "point_of_interest", "establishment"], "reference": "CmRSAAAA6_iO1R2VDp7rDUDs6eVAejX1lzWSGiddOLUjicY6qZ2aTFv8lK_vMbiogs49n02QNqH8whY1eWL-uGNlI00BgJg3g-tNfkYn3-pjnGcItqMWXe6sDb9RJgLtZvuWascvEhDzVxOsR5jRggH2qpIKTlA9GhSDdkFXMeQmWDMg3UP0Uqgz4gBdmA", "name": "Audubon Docent Guild", "rating": 5, "id": "7ddd5daf76cc4979e2ba6b062322d1c77d5d1c07", "job_title": "Databank", "place_id": "ChIJI9XyNFHbQIYRtwHb8EtTpeU", "address": "440 Wilchester Blvd, Houston, TX 77079, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.44932349999999, 29.7803218], "type": "Point"}, "properties": {"photos": [], "types": ["point_of_interest", "establishment"], "reference": "CmRSAAAAQG_Kz3XLixshWXtSkL4ONeUjAN-1IdvxNSnDTgJJZywT2mz2XBnJ1e3ior1sRSzEQ7ViDAMvnj8lvRA7SHm4wQpsJHfEs6Hy-F8XiMbu3pvevEAIVINOynERGimVhoV0EhA4VPaIsLNs3a8TnI_iMNChGhQSSUR1s8weTizF2p3iSmz8c4gZSA", "name": "Coastal Conservation Association-Tx", "rating": 3, "id": "7258b034e119f31e82320bca6e72781ee9f79d75", "job_title": "Great-Clips", "place_id": "ChIJcekacM_GQIYRPzL13cgQrPk", "address": "6919 Portwest Dr #100, Houston, TX 77024, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.47039, 29.655454], "type": "Point"}, "properties": {"photos": [{"width": 5312, "height": 2988, "html_attributions": ["<a href=\"https://maps.google.com/maps/contrib/101184977609161362375/photos\">aug4</a>"], "photo_reference": "CoQBdwAAADqfPRWOSyov_lkW6uqvKvE1gUZf3wwT41svWP3Avii9BJdJDp7JnsBWPkHVJKwv20A6-v1utlT-gTG7FSJS7mR4yq3hPUlWAiutpDYDui0Vsr8LERtqGdyLg01v1CTmHVJxpcqyNWZhalHKY1EH1XoEFsP6vh3qVyu_3BS8q_0LEhB6VLbEyn8B-H7s7cEYfubMGhT_1pxE-IDDhwshjNzSdldkwNQTTQ"}], "types": ["park", "point_of_interest", "establishment"], "reference": "CmRRAAAAU3H2a8vYwKES_0InBgvnQQadf92j1sftY0PkXdFSr76IapAg65Pc7tTmJC8-ls8wpHLPlkh4HMeaGL8hYewVIrrRJtg2PNq2JtawbySUtwGeJjgrloRF2OQo8r4-SKrkEhBY8IHX0PikJaoLV1QFxs7aGhQ1a-YCM-JO9n8YtSMaksc4je8oyQ", "name": "Willow Waterhole Greenspace", "rating": 4.3, "id": "0127506e8071350c2d48f0ca56e939045297a0f4", "job_title": "Great-Clips", "place_id": "ChIJR6_2zTzqQIYRsA7wExgfDWs", "address": "S Willow Dr, Houston, TX 77035, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.4003322, 29.7388505], "type": "Point"}, "properties": {"photos": [{"width": 1136, "height": 640, "html_attributions": ["<a href=\"https://maps.google.com/maps/contrib/117056878997299689379/photos\">Marisol Brown</a>"], "photo_reference": "CoQBdwAAAMDTSSbPAIR1VjsNHIV2IWPJ-Ps56PBqkpndgwdMIGIxj-vFtLIrvm6kon0vYSGQdjO3LiWt7jTwBMdbpFBOviGZfQPkZ9NKNIKGX9enWdIF1141aE2YsoIKzVSWRRIs1-N0P9UgZeBaZmzzKea3QCLx81VMrpn9frHg3F0GTrJ9EhDGkcQd5Rq3ZwUwif9zZaemGhRUsgKjPvzVnzj0cP4vf_QYM-YlEQ"}], "types": ["point_of_interest", "establishment"], "reference": "CmRRAAAAUjxGgHfkO_mVnQxuza5HrKScKcAM0fvPDEgFInTRLq99wtSv47BKiwvPi8pCzL0rgkcE2Nyn-nR5xi6duYUpTa89BIco-jgKsNx9rShMYwFa0NM5u02_eL7TK_yMRvRMEhA_WbYFUZrZLGBfBMlN88qTGhT4cdpG7yTHs6KzN11vH9V9Mx0JXg", "name": "Masters Fine Art Conservation", "rating": 5, "id": "a462c2eef4e22ea319485ae7b84f3d20756cbdd1", "job_title": "Great-Clips", "place_id": "ChIJp8u2bZvAQIYRbosnWz6cVmY", "address": "1612 W Alabama St, Houston, TX 77006, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.3876169, 29.794149], "type": "Point"}, "properties": {"photos": [], "types": ["art_gallery", "point_of_interest", "establishment"], "reference": "CmRRAAAAn78AOodcR2eL1Gm-wYBm4-yVoCzxonAcxmBPoysVYPS7eoUEapOmGCzxnpkSNjYuZgGjqPOV_YYQ_ZxNZoq4QCBSJBerz89esgxOVMSsqjms17wGiVvGiyKhGdxw4JneEhCehJ1E7KooTC5C4j1tXP-jGhQFzrSXjk0nTARnwSeIMGFIiiW3yw", "name": "Whitten & Proctor Fine Art Conservation", "rating": "NA", "id": "883a8c5ef35ab28e1630235ad65a6b16506a67fa", "job_title": "Great-Clips", "place_id": "ChIJ8YuXE6K4QIYRn1SF1hazFEw", "address": "1236 Studewood St, Houston, TX 77008, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.3858767, 29.7300997], "type": "Point"}, "properties": {"photos": [], "types": ["point_of_interest", "establishment"], "reference": "CmRSAAAAu11xvgMo8T2CXQWIh3NR9OFgiX3ArJDxzKFVkJvNzJr3Ta4OpD4UN12rvlOpb7ub5ShMKSBMKEJWLj-EFmnnegXULXycl1IxbiU4wEyjOmwot4EMXNY5qhMZ26sFPw0QEhBr2-ID_B5z5qO-_JKnPk65GhSb4Xs3EhS7ay6eY_9Z1KDqgGTVjw", "name": "St Mark Fine Arts Conservation", "rating": 5, "id": "ea2d4bac6d74716b33f456dff3aae0cc0b43cca3", "job_title": "Great-Clips", "place_id": "ChIJKbDEoXm_QIYRcRFBlp0dE8A", "address": "4901 Main St, Houston, TX 77002, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.483218, 29.7482286], "type": "Point"}, "properties": {"photos": [], "types": ["point_of_interest", "establishment"], "reference": "CmRRAAAAGEg7l2WfyKUnf289GQJ-u_ERCms0eZ_dxJCTd_gF4UWoIyywvnw4LsaBKEW22GKi3rbhOd8FT-zTjdzZD__VeTq2ippLFu-3-PFnQRvPpC_BFTGCrIpklcuWYIRRpR3_EhCyc07oxdq8Z-CP3_RF-mfNGhRBtnXE048ZhYDT7PNHnT2kyJZBpw", "name": "The Nature Conservancy", "rating": "NA", "id": "90af6fb9fb926dde9f7103577cebc4150bbb1dec", "job_title": "Great-Clips", "place_id": "ChIJq-m4EX3AQIYRJkn4Lhccp2E", "address": "1800 Augusta Dr #240, Houston, TX 77057, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.42318089999999, 29.7345943], "type": "Point"}, "properties": {"photos": [{"width": 750, "height": 437, "html_attributions": ["<a href=\"https://maps.google.com/maps/contrib/106788706324997826205/photos\">Erika</a>"], "photo_reference": "CoQBdwAAAJUC4zPu8QzStk1_aWcyEsqRtoeklUp6N8nMBsDNSWs_jXrgGN7Ll9wBTXILrDbTYfZva-mtuOVvCEnFhppfV87WfoZ27hTnxOZ9nvZkY4Pq7zk8hdDBY2qYSqpQuq5r63qd7Juby1PxDTR187lktjAcyCJg3k2HlDKylBVKfdG6EhA2jA6Jn8Q6gV3uHwv5bDxfGhTmKXg9Lzf-N1KVsZPAu4lvHEOuog"}], "types": ["point_of_interest", "establishment"], "reference": "CmRRAAAAO6HnGWILhhPzCPXfM5frNR3Su7R4P6QlwyzdtmBcXvI6_m4Tp-IorOgbGGvy2vLCOxungfUScHzuSWxASBsarltge3Nh5qHJcSrdgTxP7sEuUbjFgHPdGTRKVk693joaEhDJlznH_nMnnEheTF2t5wIgGhQV0cqU0pzmemUCrOddLo8tDKhkTQ", "name": "Student Conservation Association", "rating": "NA", "id": "1c5ea7722fc0d99e9f7dfca55f5d9078224d51d3", "job_title": "Great-Clips", "place_id": "ChIJQcqBXfDAQIYRErawO-goGj4", "address": "2990 Richmond Ave Suite #400, Houston, TX 77098, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-96.038102, 30.055621], "type": "Point"}, "properties": {"photos": [{"width": 984, "height": 985, "html_attributions": ["<a href=\"https://maps.google.com/maps/contrib/110279808588468038448/photos\">Peckerwood Garden Conservation Foundation</a>"], "photo_reference": "CoQBdwAAAFXMEYpX0TbbRySlFL3Y3qkIRNXdJwv6r0yLcbeIMGsiZfXElzntMQP2iH_RFdqIJe0G8j1SE_T8_67DNl4sl0KfiEiNhA1qx5f5meC4_7pDnAy0M1lt-UjHXAXdJTrKWgJ6DvU7n-kKgBAJSI9tdL1AaXG0tmhiQpTvsIo6J0s_EhC2mfYowGLNcmOOkbMs8qRtGhS9VQ9KQ72_7DxLFPIKIL_kNds1xQ"}], "types": ["park", "point_of_interest", "establishment"], "reference": "CmRRAAAAZmo4PMOlo5WsfNFRmSjgUo1uzEO4cwgVbA4T_BfjIK6N0cWxVleGQv2QdPnb9LSdvlPFM2d5oMyOqX3j4LVKlMj19tsHwYIPIvCHLUIN3d5M43vtkXJSS21jlrlpts3eEhCkQfg9vHGnorE1saofNhAUGhQinH9_HwRoTff1B3mu7A8hthoJKw", "name": "Peckerwood Garden Conservation Foundation", "rating": "NA", "id": "e618a4c618cd67ce4f5fdc165f640220ab3b53b2", "job_title": "Great-Clips", "place_id": "ChIJmUR7pvHKRoYRIIl0o73bPGE", "address": "20559 Fm 359 Rd, Pine Island, TX 77445, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.64386449999999, 29.7515036], "type": "Point"}, "properties": {"photos": [], "types": ["point_of_interest", "establishment"], "reference": "CmRRAAAApdGXbrHK5RBiSe1rKKxRbwESaxr7FOjb3e5PuWL523d6Gq5oSKmy8Eg1EHkf_An67Gym3JGzR1XZIPR2SCdjPaxejQLjjkzgJwO0e9YIC_TcpVXfikHoidmV_9m2GD8oEhCRitkOsEY-rJDkAmN4O71IGhQv46DCf9f9j3FPOa6oHdVAITIlbQ", "name": "H2O Conservation Technology", "rating": "NA", "id": "30c07988ef8dfc62dac712b9d587daa4a36f2539", "job_title": "Great-Clips", "place_id": "ChIJIWZRKeHKQIYRXxta3wOMGGc", "address": "1725 Hwy 6, Houston, TX 77077, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.5705632, 29.7714443], "type": "Point"}, "properties": {"photos": [{"width": 3024, "height": 4032, "html_attributions": ["<a href=\"https://maps.google.com/maps/contrib/108143329814504597326/photos\">State from Jake farm</a>"], "photo_reference": "CoQBdwAAAF18hjc0VGN7IdLVvUFu-0ksOzau85uDJdxrmrGQDN4Tgh7iIHrx713tOUHfMNvgtGlFgzXL8c5Ns0u2mqRJOtGGUbJYCQcs_XJZk5Bez8oLJj27TOjfYZKAEcZg-ZFiHd01hIIqOHpx1Yh1HpsDerZqqY-y_RclzRHomFtIVWBnEhD0z1np-mksKOpRWmOHB6T8GhS0A2EkELVBUnybt7vkuUpXwvZJjQ"}], "types": ["park", "point_of_interest", "establishment"], "reference": "CmRSAAAAnLBpEiSG5WRgdFUYFL63krgXue_E8L7CAGxfe9Md8_V4AMoJa9tF8YpIRKCiiEaxgGWPkE9NjpPUrdW5ryjGJCvToqR-_2ivPMWcpm0U7pQw_bN3YINMo5wNZZRuNvlnEhBCbvKnFRhX1UVGDkMnc993GhSkHhlk1Gp5rfrW1wdEY9zNXOtFbw", "name": "Houston Audubon Society", "rating": 5, "id": "050a5458d86bdd1cee7b09678bd6256d0a20a73e", "job_title": "Great-Clips", "place_id": "ChIJlQOxwVDbQIYR2uX_TZl0TYc", "address": "440 Wilchester Blvd, Houston, TX 77079, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.56820189999999, 29.770778], "type": "Point"}, "properties": {"photos": [{"width": 1800, "height": 1200, "html_attributions": ["<a href=\"https://maps.google.com/maps/contrib/108765250995932379967/photos\">Audubon Docent Guild</a>"], "photo_reference": "CoQBdwAAACYQ5JX4zBjy1ZwzHYn_dplS0Nt3-gQ1cdSD_Hc-vlKB9LFJcJEPB1HH8l4FoOResuBbKKpM3l4F1mbGcJCkchqE8O8hVoBnZJs1F3NUgcOcoCsKwPWJrCwY7K5k9-CJzSm-7rK58PDoul4317pwknS3Y3pf0mHDqAi9LR4wuLAbEhBHTzZr7jsTH-j_eINUjMqLGhRxaPt0YZVL_aff3LK-B_pVsl9-ag"}], "types": ["park", "point_of_interest", "establishment"], "reference": "CmRSAAAAiAwW7v8HBuEkFAjaCNW9MpwFN3aFq-dQ6Kz7q3CY5Tqpu1p5OhUojUkZLE8IzfY4Fir3xWAOyWzEOHrrs5uMkOcS1PZYxEE0ykkzJMPyukU7f_iZk3dukHqFANNzek_pEhBBNm-hGNft227tVbm-1NESGhQwiKbkQ-pXNcSRh5HxXWX8SpO0uA", "name": "Audubon Docent Guild", "rating": 5, "id": "7ddd5daf76cc4979e2ba6b062322d1c77d5d1c07", "job_title": "Great-Clips", "place_id": "ChIJI9XyNFHbQIYRtwHb8EtTpeU", "address": "440 Wilchester Blvd, Houston, TX 77079, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.44932349999999, 29.7803218], "type": "Point"}, "properties": {"photos": [], "types": ["point_of_interest", "establishment"], "reference": "CmRSAAAA5G7LohfbwRmV2S50KNxhrMO4-Rg5-HQjYaTlUwINFpJLWvsSvlRtUm8Yk4oQUETXtxolz56hjsayZmpxKpV-jcJTIEPYwtd9IXN5YveP2CCy_UNfk48GAyaRdxTPmeAcEhAsBLINRAmsDwT8MzbHT136GhR1nuUMfO9PPSB9ySeTbHVH62s-0Q", "name": "Coastal Conservation Association-Tx", "rating": 3, "id": "7258b034e119f31e82320bca6e72781ee9f79d75", "job_title": "Kinder-Morgan", "place_id": "ChIJcekacM_GQIYRPzL13cgQrPk", "address": "6919 Portwest Dr #100, Houston, TX 77024, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.47039, 29.655454], "type": "Point"}, "properties": {"photos": [{"width": 5312, "height": 2988, "html_attributions": ["<a href=\"https://maps.google.com/maps/contrib/101184977609161362375/photos\">aug4</a>"], "photo_reference": "CoQBdwAAAMVs6rMeIukB5YuzYZahVU_VtFoQG2yl5mEg4gLWS89YGRf-yjenSBv77veVkkvsJupKEYGyuNtYSMQH0xIJ3dM3OUaZB3z8HNQuof00F0gtLVYeemFWUHmtiuWVQcfQ92Ea_Tv0TTbU5_Y3eZWvgZ87en0ivNAeY58SDrQOShLoEhCr_CkQl38WZV4ce3s-RVBLGhQFkL1BMz2JwzZZRvyYdp-AuXCnAA"}], "types": ["park", "point_of_interest", "establishment"], "reference": "CmRRAAAAVXH6_BI1vRaDMAY9AcfgyRi4z9_kdOHG-IQTy9vnZDiYD7HYvPt5fnCFZGnoHQrHDWancklWC2SflaJC4jEN0PhP6XM2Gay6POVR2LAHCLU9J7esvffm8oIwv84A7u6XEhDS5Yq-AWszu0XI12LIno5SGhTCeXc3kpEXo4_BDxx6YfoLCjbDyQ", "name": "Willow Waterhole Greenspace", "rating": 4.3, "id": "0127506e8071350c2d48f0ca56e939045297a0f4", "job_title": "Kinder-Morgan", "place_id": "ChIJR6_2zTzqQIYRsA7wExgfDWs", "address": "S Willow Dr, Houston, TX 77035, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.4003322, 29.7388505], "type": "Point"}, "properties": {"photos": [{"width": 1136, "height": 640, "html_attributions": ["<a href=\"https://maps.google.com/maps/contrib/117056878997299689379/photos\">Marisol Brown</a>"], "photo_reference": "CoQBdwAAAFISuSMvtHR4uG-mPVQi4RbZmpAKxEHLpoA2OUBbv5T6G0SXFa7ykr9AG8xIJ_2CDw24IYz6IkAfnn51Ir-UClZQURWbj8DkIO-Rcp9nM8HPRjUpbDgNRhS5-upYauh87ZxyFbSMwDvSz3t9rBPB42neGINSXuqwHu7xb3t9_misEhC-JFEFo2L7ttqNDgOjy4owGhQg_-Cn5cMo9O0QsKO-1-OgnifvfA"}], "types": ["point_of_interest", "establishment"], "reference": "CmRRAAAAwpzfLNpLbCV_OIFoAPy7w0r7HVgC48UBL0bGeQMsqw9WGgFHCx0dB7YywlvQwTxeTW5aWz8tYeZQdOHJWR4EefOvOEbjdffImenXSdLvwIsl1qKUfr7x4HfirhMaqTQSEhCx9cPSP496bbNGpDtOT-hXGhRxg7HokbHuA8SyU0WYgkImVoiwoQ", "name": "Masters Fine Art Conservation", "rating": 5, "id": "a462c2eef4e22ea319485ae7b84f3d20756cbdd1", "job_title": "Kinder-Morgan", "place_id": "ChIJp8u2bZvAQIYRbosnWz6cVmY", "address": "1612 W Alabama St, Houston, TX 77006, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.3876169, 29.794149], "type": "Point"}, "properties": {"photos": [], "types": ["art_gallery", "point_of_interest", "establishment"], "reference": "CmRRAAAA4zJ-p_8tL1Xir8iAU5kPv2GRbQ_U6WKGM--fU-pBFfZ0liKKAWngv1ze7HXbq2P5qPrbey3WmELGbDGJtRZD1f0wKtlUqBlo8IPWOLB3DYjrexV8i1h0FkhlNmvsOyiLEhD98kxr9YG8vgfCLDBhJUECGhRGREFTg5vfXKUIqwVwweJAikOE8g", "name": "Whitten & Proctor Fine Art Conservation", "rating": "NA", "id": "883a8c5ef35ab28e1630235ad65a6b16506a67fa", "job_title": "Kinder-Morgan", "place_id": "ChIJ8YuXE6K4QIYRn1SF1hazFEw", "address": "1236 Studewood St, Houston, TX 77008, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.3858767, 29.7300997], "type": "Point"}, "properties": {"photos": [], "types": ["point_of_interest", "establishment"], "reference": "CmRSAAAAhD8A2b2GCVXgAKa4jd216Qro_wfjvNQciMkjcDYwrutNLTMAXurygI-scdqTIcPLgXCJDO_Af-f3GLNE2YjccNiw9-t8xf4TedUvKv2kDuTMEfJFiEXverS2Ws1Z-x-pEhAdi_TLKcljVPMgEhmB_57pGhRR3z5pDvvBSBCtqW4PRkV79uKJHQ", "name": "St Mark Fine Arts Conservation", "rating": 5, "id": "ea2d4bac6d74716b33f456dff3aae0cc0b43cca3", "job_title": "Kinder-Morgan", "place_id": "ChIJKbDEoXm_QIYRcRFBlp0dE8A", "address": "4901 Main St, Houston, TX 77002, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.483218, 29.7482286], "type": "Point"}, "properties": {"photos": [], "types": ["point_of_interest", "establishment"], "reference": "CmRRAAAAOYJk5K1HPA3XveCXMjmBmK0Z3ddUWIwH10HtICuO6hW4TDF5O1XLx5ebshF_6YernnUdLCy4T2S9tduMp5J-fngZKHUMOO0Jh4vmLIOpy9ci_MaOVl27Z2rBroAuf0wNEhCEZfQZ8HgBBc8VHcX9z97pGhQiNg2dwvG400m4HV7PPwxWyMkfrw", "name": "The Nature Conservancy", "rating": "NA", "id": "90af6fb9fb926dde9f7103577cebc4150bbb1dec", "job_title": "Kinder-Morgan", "place_id": "ChIJq-m4EX3AQIYRJkn4Lhccp2E", "address": "1800 Augusta Dr #240, Houston, TX 77057, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.42318089999999, 29.7345943], "type": "Point"}, "properties": {"photos": [{"width": 750, "height": 437, "html_attributions": ["<a href=\"https://maps.google.com/maps/contrib/106788706324997826205/photos\">Erika</a>"], "photo_reference": "CoQBdwAAAL0Kp9Jrrb8YvUtCs1JifvmGNz5qym1Ua0fK9iMV7jBvhamk9JFhj8MDG5RpDu45AmowlUf5qmiN1cYCwHgmuKU5VF8NWHtjJBrehRoWScLJObwXAric-_tZzHe-3penI8KasF50Kgmm9Xc-30FVuPYoUUumDUeDkXNFn2HiuU8vEhAtSHXjWkzJFmmzoSHlYiQeGhSn2-jLZMjFvuTJJDwL8Y_xKQfVGg"}], "types": ["point_of_interest", "establishment"], "reference": "CmRRAAAAVlNTPzaL_GdRSsnIT-m_MtKmhQauFdK6QJI9XQJDaVuvwexuzt4dGdoVgwktpk4yuzdLYFU1_Wr4z-GJ555o--Qvy0xIaHr7z6HBFTOA6yndFzd8EBEGuS_qnB8g64BWEhC-vV-tCI6GF1GYuJZkApv5GhTc8q2OCn5qmWFaXqwh7wtp1ktHbg", "name": "Student Conservation Association", "rating": "NA", "id": "1c5ea7722fc0d99e9f7dfca55f5d9078224d51d3", "job_title": "Kinder-Morgan", "place_id": "ChIJQcqBXfDAQIYRErawO-goGj4", "address": "2990 Richmond Ave Suite #400, Houston, TX 77098, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-96.038102, 30.055621], "type": "Point"}, "properties": {"photos": [{"width": 984, "height": 985, "html_attributions": ["<a href=\"https://maps.google.com/maps/contrib/110279808588468038448/photos\">Peckerwood Garden Conservation Foundation</a>"], "photo_reference": "CoQBdwAAAEdir8g2wK_AWZVYbFlwfimxgelyY7LLlvxsisAMSFOrEOvluiaGtqmOa_VDDeCJ3v5hRUlTgJYqR5sie-HzoYM5gtIf7-ZMTh5y1EEPkUHx7pmgu0N_09iiCs56c1yEvCvoUhqmPhtLFg7edXcyOnr6zyeklwvgQVqCmCf1hbKgEhC3gRKAa4oQueHnbQ9A0BVNGhTKtZZF32imFC5hlBEDBRnfiZex3A"}], "types": ["park", "point_of_interest", "establishment"], "reference": "CmRRAAAA4jHLKnxqrMY2QsCElYOSsBymHS6yZudEx9b8ng_S2WYY4U1ANOvjXBi4suqAfEbfKYNZomopavRLgzBCluzwbDuAeeIMWPh2iDoXIl-jxJLyqwsDBXNKG3C_IZfy1160EhDbbHBpUjn5mw1pI3CSsSDoGhR3rMNazkLqUFt6l5RIeWTOPUJ-gg", "name": "Peckerwood Garden Conservation Foundation", "rating": "NA", "id": "e618a4c618cd67ce4f5fdc165f640220ab3b53b2", "job_title": "Kinder-Morgan", "place_id": "ChIJmUR7pvHKRoYRIIl0o73bPGE", "address": "20559 Fm 359 Rd, Pine Island, TX 77445, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.64386449999999, 29.7515036], "type": "Point"}, "properties": {"photos": [], "types": ["point_of_interest", "establishment"], "reference": "CmRRAAAAK1sBUg7E_FnDueYsoLOikTzMmVK2f3NZR_ARy4I3qHFQanekGibA1MAZgLKbDMPhTrawOJWC-AT8thi3sCJpKiiwJuakelq0IsbQS3QXZayTOHRHsS4OUrt8bNUaVgr_EhDIcMxLI0ryo8rXpEfy4ticGhQpE2VoVQ5M25qOrDdF7cg5DWY93Q", "name": "H2O Conservation Technology", "rating": "NA", "id": "30c07988ef8dfc62dac712b9d587daa4a36f2539", "job_title": "Kinder-Morgan", "place_id": "ChIJIWZRKeHKQIYRXxta3wOMGGc", "address": "1725 Hwy 6, Houston, TX 77077, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.5705632, 29.7714443], "type": "Point"}, "properties": {"photos": [{"width": 3024, "height": 4032, "html_attributions": ["<a href=\"https://maps.google.com/maps/contrib/108143329814504597326/photos\">State from Jake farm</a>"], "photo_reference": "CoQBdwAAALp3m6osi_uoTnPd8MypNCFBui5GbWzZAx3wnrNlad67lurrFDB0dSDt_QPsobWnzyP5K21TuNfN1w5w7rAghJ5DTbfao3qHuGbu9bl3viKraUAu9GyMSRB2mIWpe2TG-Jv44Wf1mOP0rP_KHZWK_1mccZYkCE9Q0co5H5CnIe2GEhD42rtI6ZV8OPB_YVOsWGzcGhSD192YGjBjaL9IVNP5eZpeqPIfjQ"}], "types": ["park", "point_of_interest", "establishment"], "reference": "CmRSAAAArYNBV1IGLplE9u7b7BF6xMf-YgqSi_6VWzhNDzOqPIODQGXV23tti_fi11gmb8tly47JLEBuz3hnmsSXVShok69vsaXgJwIPK_ZCUfLPUF-l05OdPyoOaoh1dVRH50sOEhAEBkU350iZA4wVWDB3InduGhTCKF1IkeP7k3f_a4LRq5V5Rj3IRA", "name": "Houston Audubon Society", "rating": 5, "id": "050a5458d86bdd1cee7b09678bd6256d0a20a73e", "job_title": "Kinder-Morgan", "place_id": "ChIJlQOxwVDbQIYR2uX_TZl0TYc", "address": "440 Wilchester Blvd, Houston, TX 77079, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.56820189999999, 29.770778], "type": "Point"}, "properties": {"photos": [{"width": 1800, "height": 1200, "html_attributions": ["<a href=\"https://maps.google.com/maps/contrib/108765250995932379967/photos\">Audubon Docent Guild</a>"], "photo_reference": "CoQBdwAAAGdAeKtz6CPFfTIUoZJfMa3racDvem2wzeXwT32Fky34MmklnjFGRkbsEvDkP50kxXGzBy1g1YhJya8Z7KpjCulo7rSBB42nmg7uIqaUY2HB0BjxRJO62Bt-ZZJIz7ank81l2SyTDI0lTJhk11k3Pi7sVY64TKe4EymDJf-hmZS4EhBqhPXtOfD_1aCBf43AlYoYGhSEBYEAWymdNTLyLyws13xhxE6SQg"}], "types": ["park", "point_of_interest", "establishment"], "reference": "CmRSAAAAxvSe1Uj9a9Xqpe9L6EMmcBtzI7iqhRMRkXx_sUECsnFhQrWOsGbZuTRR62R6dO3ZObyRN0Ys5zeFLH_ThqkJdw23TcY15GLp295V7VZIyGddu4Li5QlunI80WyYqgkBSEhC0H2xbSPR2LWYtiO_I-6RkGhS_WEjQ76QKu5LZDmfbJSu6gPLylg", "name": "Audubon Docent Guild", "rating": 5, "id": "7ddd5daf76cc4979e2ba6b062322d1c77d5d1c07", "job_title": "Kinder-Morgan", "place_id": "ChIJI9XyNFHbQIYRtwHb8EtTpeU", "address": "440 Wilchester Blvd, Houston, TX 77079, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.44932349999999, 29.7803218], "type": "Point"}, "properties": {"photos": [], "types": ["point_of_interest", "establishment"], "reference": "CmRSAAAA4vp4Foszr1fRqI6IMlNi1gfHS1QZ8Ner0zdM1H4JCSjz786_c8njcI11oHdQ_LhYjIOEa5V3g9tzeAXrfBYtkNK8_Jo4kqCKycLdi6Fxa5LkjcNSJ1r3xMFLJVj7nG90EhC4IV-gPRBfY0kFQn9wl6nvGhRERL9shXVY7s7N-d3oSyBbp_jv2Q", "name": "Coastal Conservation Association-Tx", "rating": 3, "id": "7258b034e119f31e82320bca6e72781ee9f79d75", "job_title": "Occidental-Petroleum", "place_id": "ChIJcekacM_GQIYRPzL13cgQrPk", "address": "6919 Portwest Dr #100, Houston, TX 77024, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.47039, 29.655454], "type": "Point"}, "properties": {"photos": [{"width": 5312, "height": 2988, "html_attributions": ["<a href=\"https://maps.google.com/maps/contrib/101184977609161362375/photos\">aug4</a>"], "photo_reference": "CoQBdwAAAN54kwK_V3DV6n49XMqqh18I01n6L02OcPWtLs7XBAXj5t4kKyW0xk8l69gFTTg9LFfstLZFMymXAGhi-626ujaVY-X5fNb9w7gA9bh5U8B1Z89ToWo1tMPAoimtDWApdX8t2fNcatiyeH4EjQiakzgtou2IZpKyggoUf4uCYiKsEhCOD9hDEKcvsFBZoYAu7ELaGhSyhhC4H7jN-Cj-qLblG6rPG-ui-w"}], "types": ["park", "point_of_interest", "establishment"], "reference": "CmRRAAAA4CY7tjdKaG8xGWprUEUfzP6ym1uyYneNMbA_-UwMlzc28LOmjJzYfzg2pLJqBAfVJaeMtrhx2ZDpM29IdJkVg10LTePrhK2mChoPCdJvyTknLoqQwdvTfhlw9XL8aCbYEhA3Bw8GeubCx8SDM_KqDzrJGhQR7IikCY21KSnORzbatz5mPWyYPg", "name": "Willow Waterhole Greenspace", "rating": 4.3, "id": "0127506e8071350c2d48f0ca56e939045297a0f4", "job_title": "Occidental-Petroleum", "place_id": "ChIJR6_2zTzqQIYRsA7wExgfDWs", "address": "S Willow Dr, Houston, TX 77035, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.4003322, 29.7388505], "type": "Point"}, "properties": {"photos": [{"width": 1136, "height": 640, "html_attributions": ["<a href=\"https://maps.google.com/maps/contrib/117056878997299689379/photos\">Marisol Brown</a>"], "photo_reference": "CoQBdwAAAOplLeTvtNYjiAY7-XE_eXV_fymnV-EKuS1IwYKnGxXxAPLJtlepZfi2oEGN_q6NScAdDYVKIenys83AD2ckoePbo7QwMe1rT45rpm2_92_E-op5JYhYoghNS8SlrxBrpWZo5KqBjTKwxNKWp-iFNF8k5de12yJw9hZXZOOS2NTjEhAu4BoAmoOhSR1yV-0s7XOAGhRwJ8Sp0oZxU-98HYnWWvbXev_YAQ"}], "types": ["point_of_interest", "establishment"], "reference": "CmRRAAAA-IKDD1yoXTjhNxkl5PY4FUMgLLS8Ge4FRwvsSzOhaTqudv_OiN6G1UvgxgY6x_aQag6IhlCbKPIxJ90Ep1QN_Zq_DiK7UIBRAiSjP-MArSUaql3le2QrIriBhi9A1YHvEhDMcWdSkDtt-VtIC5Yd0su1GhRjm9jDlhyM4Ypzuc-2ghUmfv2AYw", "name": "Masters Fine Art Conservation", "rating": 5, "id": "a462c2eef4e22ea319485ae7b84f3d20756cbdd1", "job_title": "Occidental-Petroleum", "place_id": "ChIJp8u2bZvAQIYRbosnWz6cVmY", "address": "1612 W Alabama St, Houston, TX 77006, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.3876169, 29.794149], "type": "Point"}, "properties": {"photos": [], "types": ["art_gallery", "point_of_interest", "establishment"], "reference": "CmRRAAAAiVV8T8fEvw6wXEMcuiklCULYvwFv_yUnnor3apiTuONRwzivr8ghtgzt35Z5bnJnwkRrTYOw5_ZqYlun6MHWidICOVZL4mrFYYEOIQwKFMxl6_hjxBLd--_p_AIEGKwHEhDBu-HhCwWVslVTBZJ6qvL5GhSsyk55OwjblqROJ0hbxQxWpXzyxQ", "name": "Whitten & Proctor Fine Art Conservation", "rating": "NA", "id": "883a8c5ef35ab28e1630235ad65a6b16506a67fa", "job_title": "Occidental-Petroleum", "place_id": "ChIJ8YuXE6K4QIYRn1SF1hazFEw", "address": "1236 Studewood St, Houston, TX 77008, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.3858767, 29.7300997], "type": "Point"}, "properties": {"photos": [], "types": ["point_of_interest", "establishment"], "reference": "CmRSAAAA615zRPQnBjjoyEzGv8lVuk6sPvC_JbWVpIw9kwBVbUjA7R2jXMJMcUCR6-EvhtkmBWPxXPkHI9XpPXilu2zk9WciHNZNcjUqGygyfhQ3IHjIXWY7o9sQxu7_yZj3WSdYEhAnCUPmHO01rWsNAYO6Mhl7GhTtZonp3MSdmkrbRmy2v2IBY6PHPQ", "name": "St Mark Fine Arts Conservation", "rating": 5, "id": "ea2d4bac6d74716b33f456dff3aae0cc0b43cca3", "job_title": "Occidental-Petroleum", "place_id": "ChIJKbDEoXm_QIYRcRFBlp0dE8A", "address": "4901 Main St, Houston, TX 77002, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.483218, 29.7482286], "type": "Point"}, "properties": {"photos": [], "types": ["point_of_interest", "establishment"], "reference": "CmRRAAAACj-PSReTYkmuDBOAA-l-nMzMSHnTWlH7iaAAFebMEfrULKJaFogX9xSLlIFFUBd5TNS3UgA5R2m42nK7vM8NQdNWSYvCdrCDxoqtJ-XeTQ1pCyN9dEs0zIh4DZ1dCkBbEhCGF8PHmXjsN_5qJgfUrRWcGhT_P7k2dM1Yd8QNU80Xs4QXyyA2Lg", "name": "The Nature Conservancy", "rating": "NA", "id": "90af6fb9fb926dde9f7103577cebc4150bbb1dec", "job_title": "Occidental-Petroleum", "place_id": "ChIJq-m4EX3AQIYRJkn4Lhccp2E", "address": "1800 Augusta Dr #240, Houston, TX 77057, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.42318089999999, 29.7345943], "type": "Point"}, "properties": {"photos": [{"width": 750, "height": 437, "html_attributions": ["<a href=\"https://maps.google.com/maps/contrib/106788706324997826205/photos\">Erika</a>"], "photo_reference": "CoQBdwAAAMOnmoKlRt5LugGZ8e83OUwZ0svxsBvMBzSi1XCNjICw85uBEXqXiT0BdV-uv4ELIuDiwCvgKB8xsi9yRff8sa9U0aXyRv3aEVooH79Oc8BaGOvkmsVkr52MOK7hFkyNDQqbqHpMGEc1U5xdA_fCvc_ltpFW3COgsBK5LoOhQCntEhCyPHmllJXPydbhlWHLvRTWGhROWVtb-V8YghuvmAM_dK_gpfHmdw"}], "types": ["point_of_interest", "establishment"], "reference": "CmRRAAAA_4h7qxQ_wSOvgpdpp4555lYwjaLHwakzdSLLm_BXDBvdk0HDF-VffocEs2m1qg476WFiUcXKHRv7Mg9wDZRv3WCqtdslJrY6M_h-w4OW8MQSZrk6bdfd9gx3QBWYwUGxEhC7ZbgfOp1zsGP1gb9-sleKGhQ9llBRwNFbCH6tPI9cu4KiJvqkew", "name": "Student Conservation Association", "rating": "NA", "id": "1c5ea7722fc0d99e9f7dfca55f5d9078224d51d3", "job_title": "Occidental-Petroleum", "place_id": "ChIJQcqBXfDAQIYRErawO-goGj4", "address": "2990 Richmond Ave Suite #400, Houston, TX 77098, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-96.038102, 30.055621], "type": "Point"}, "properties": {"photos": [{"width": 984, "height": 985, "html_attributions": ["<a href=\"https://maps.google.com/maps/contrib/110279808588468038448/photos\">Peckerwood Garden Conservation Foundation</a>"], "photo_reference": "CoQBdwAAAPtYYwh1XxSk7gGvZuLcTT8nLvmR5huXuR3bhubK9Q8noLvyyNvYhKCNpJuaDIQ1eizbVRb565sDoPGRwu3bn9HIJQJeRGrq67odhy7zFr1lZaDPtQULl0g_dFh880zlt-RH1Iyn9YK3p1Fc5z4tuhicddViYKMwvHT4IW1RpQj9EhBnGQD-WAZeF5qOBgzkaFuuGhQZEseP263gtfa1OE3feRfb3JxI2w"}], "types": ["park", "point_of_interest", "establishment"], "reference": "CmRRAAAAJ2RS5XvFYnkjUd7y9qLkFYLKUXqncglI69aMM8pdjuCr2yvbF6gVSIjVK0jFv3vVvTzkgI8Bx0-5u3NyrfKcT_iwDyFFKvM1MViRt2nYGX7xVngB3IoDjYhy73pvzG_6EhD0ZyNVvr7BE6TOAErGIHVyGhSwf6mCZrQvDdoOhHG1aqV4Kw0O3A", "name": "Peckerwood Garden Conservation Foundation", "rating": "NA", "id": "e618a4c618cd67ce4f5fdc165f640220ab3b53b2", "job_title": "Occidental-Petroleum", "place_id": "ChIJmUR7pvHKRoYRIIl0o73bPGE", "address": "20559 Fm 359 Rd, Pine Island, TX 77445, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.64386449999999, 29.7515036], "type": "Point"}, "properties": {"photos": [], "types": ["point_of_interest", "establishment"], "reference": "CmRRAAAAOTLE2itiY7lg7x-Vs9-lI1rrqdvo1LyxWhzdRrfUy96HBSvqb-Uus_v3lLyoRQDWJWBbSIwVwqhwDnRcKJDeYzc6AW7NmH8ZWmgkQWBU04u1opXG-ZSW_Ei2zmYKpXI1EhBfxFkV287GxKlIpCXm7fejGhQ_tlM-VFc1xGwCrcx5E-i_1SOiUA", "name": "H2O Conservation Technology", "rating": "NA", "id": "30c07988ef8dfc62dac712b9d587daa4a36f2539", "job_title": "Occidental-Petroleum", "place_id": "ChIJIWZRKeHKQIYRXxta3wOMGGc", "address": "1725 Hwy 6, Houston, TX 77077, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.5705632, 29.7714443], "type": "Point"}, "properties": {"photos": [{"width": 3024, "height": 4032, "html_attributions": ["<a href=\"https://maps.google.com/maps/contrib/108143329814504597326/photos\">State from Jake farm</a>"], "photo_reference": "CoQBdwAAALanKM2kWWsaHDunP2Trgc7KqKFM9RU_3qMdm8WI7psE3BIwynMIdGJQpQpcjWVHbbW-gKIvSEf7Ir7cWTDpgrPeN075QatJJRDLzvWyazy1oQfl16K34xSuhlwViUU_eZyD5s1Vt5SR1MAbiGNDktS1Gzdwp9MBsQbZr34vCQFkEhBIBAyCbO2p_jUfP33BVjMSGhQl0hPlEqFC3gnHgWVxSMKvRugqWQ"}], "types": ["park", "point_of_interest", "establishment"], "reference": "CmRSAAAARr5tz-IXpCjcmHkp_Z2ydqRAMgZPXbd2cR2e6QvZr0yXCasdao4-PrvcfUsgwonM8ouFsaURiqGTTK1BD72QTjxSyh5dYyXnbkCHvPuDWBdtQTQ0cwQBKrf9DX5GkPjWEhBs7OuwcE6ElhOdaDouI2XuGhSNa4PMlHFudvfKIcj_daCAKkrhKg", "name": "Houston Audubon Society", "rating": 5, "id": "050a5458d86bdd1cee7b09678bd6256d0a20a73e", "job_title": "Occidental-Petroleum", "place_id": "ChIJlQOxwVDbQIYR2uX_TZl0TYc", "address": "440 Wilchester Blvd, Houston, TX 77079, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.56820189999999, 29.770778], "type": "Point"}, "properties": {"photos": [{"width": 1800, "height": 1200, "html_attributions": ["<a href=\"https://maps.google.com/maps/contrib/108765250995932379967/photos\">Audubon Docent Guild</a>"], "photo_reference": "CoQBdwAAAPfg2_mdMn4-7Sv7vX_BFIiojMkF5t8FYxuZeIR3jS9IjC22Nv0kOhdKbG5Q7kjJcYAzOHjTmrDVTVwMF1RkEgj9Ey1S8zqIRnrzXeCSWA_VhahOoOL2EL6Eft0IhE3aH4xz1mVne-uVo9CIB1ynsTQER76uVqISwbblvvOoLvHTEhBl0FCjcrRu3g0XJu4ifd0KGhSSPiOGzJzBRrNKXFOLOA1ulA07gg"}], "types": ["park", "point_of_interest", "establishment"], "reference": "CmRSAAAA21CYK82m9HVyA776-5kqC4n1CndYBfT5_WQPgSaLM_7fDEFNi8go5XlJGW_IaaBKqvLiBNfGcZBvswS5ThU30Ly0TKoTozxfqIFM41jerp5j_L8zL93LtezRLnPrIq7wEhBPJJC5nI07ip_o2S72WHBIGhTMFNPF5pSFQXL8LSRvTEdJOcyHnw", "name": "Audubon Docent Guild", "rating": 5, "id": "7ddd5daf76cc4979e2ba6b062322d1c77d5d1c07", "job_title": "Occidental-Petroleum", "place_id": "ChIJI9XyNFHbQIYRtwHb8EtTpeU", "address": "440 Wilchester Blvd, Houston, TX 77079, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.44932349999999, 29.7803218], "type": "Point"}, "properties": {"photos": [], "types": ["point_of_interest", "establishment"], "reference": "CmRSAAAAkDw5Xp-5FkRl-PVvyEzPCENb0W1Nbj3DFEA7khlr-vL7f-VJ0pxunh7QQpdTc5gsVyALLPZfArS4SbCO1eBDRZr0Ly-dFFtlFZg_D4P2fySJ3KhKluYus_9abxMbf-BDEhDvXENc8RavzqrPX6v628nQGhTCuzfAGZu4XpUNyyROyB-v7goxVg", "name": "Coastal Conservation Association-Tx", "rating": 3, "id": "7258b034e119f31e82320bca6e72781ee9f79d75", "job_title": "Roto--rooter-Plumbing-%26-Drain-Service", "place_id": "ChIJcekacM_GQIYRPzL13cgQrPk", "address": "6919 Portwest Dr #100, Houston, TX 77024, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.47039, 29.655454], "type": "Point"}, "properties": {"photos": [{"width": 5312, "height": 2988, "html_attributions": ["<a href=\"https://maps.google.com/maps/contrib/101184977609161362375/photos\">aug4</a>"], "photo_reference": "CoQBdwAAACA9P5GRf8yiNyzfxeCUgUoKeS38fBktFrfFTYwzxqyCssokbDJJ87PeTr5tBXC0Y_qftjptktQb6CawPgd1ExQgJ1CH-frkNxS5In5aKdEl5o_nUmVuwhm4b8Dl5Mtrzx8lbrKgj-JtgFdDNJesNBYNtT4FiowFF2zZOc48jLyiEhD0NfvDFsI5bCESoSUW7m9AGhQn1RWvW_v3ogTqZ5z9nwqIIrLajA"}], "types": ["park", "point_of_interest", "establishment"], "reference": "CmRRAAAAPRchBLl9pMtVAauYPAeynu8tYsi6rXuvMK3IgSxi_uVb3kEEAuVHAPUb0fJ0XAhreZga8MxL879zOO2vrJqxPUmLGwGwkayYu-DFcK4Y7V7jnp-qqqUvgYdQ2bkR4jzdEhC4ixV9hfVrhcN2Csm86rOeGhRDlDJneAz4NRAYE6dyt8PIh_UYZg", "name": "Willow Waterhole Greenspace", "rating": 4.3, "id": "0127506e8071350c2d48f0ca56e939045297a0f4", "job_title": "Roto--rooter-Plumbing-%26-Drain-Service", "place_id": "ChIJR6_2zTzqQIYRsA7wExgfDWs", "address": "S Willow Dr, Houston, TX 77035, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.4003322, 29.7388505], "type": "Point"}, "properties": {"photos": [{"width": 1136, "height": 640, "html_attributions": ["<a href=\"https://maps.google.com/maps/contrib/117056878997299689379/photos\">Marisol Brown</a>"], "photo_reference": "CoQBdwAAALAQFvglyx3yKKAQ5tcVFgDHvN6sLGXqp6CVCKasLIXYssixjRgIYotW8gsNfQlaB_VJduS_GWtmt9cIoXuKhrrScg8IvTbm2BlSO-mauRqgcZCGmvvuR8HIGLSTsinvLu2bX5Y2Aq7gJO1KiX51XH1cDt3ExfjeyStM_TZa_popEhDJ0puHwSsBrki9__KLehXEGhQDQN_b3fsKY1F6UMFzU6h6ycgJaQ"}], "types": ["point_of_interest", "establishment"], "reference": "CmRRAAAAAaTRH43QTicUQt5UVgrKtbqtgWTQmXLxO1BgwilXaScQN-RB0wJvYfBC4xd8A3JBGtz41utf6iRtcyaYou60hrcj2CEh_eDR3jOLT0zgsBwIQtTMjGu-psHjqjVqAw9qEhBI3P6hUD8Ipj9lSLjsy3IlGhR3u6tTPIRlKNYDbNHRnL3ivGTDQw", "name": "Masters Fine Art Conservation", "rating": 5, "id": "a462c2eef4e22ea319485ae7b84f3d20756cbdd1", "job_title": "Roto--rooter-Plumbing-%26-Drain-Service", "place_id": "ChIJp8u2bZvAQIYRbosnWz6cVmY", "address": "1612 W Alabama St, Houston, TX 77006, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.3876169, 29.794149], "type": "Point"}, "properties": {"photos": [], "types": ["art_gallery", "point_of_interest", "establishment"], "reference": "CmRRAAAAyprMoo9iLB2XVkyUxJRcij3_3PfdUKxQfKfVwtpPNZtL3jeFzLdhE9mLg0f-CyME6B02wZHkwA7RtWLm5WQN2YN9eQkOeYpapDcX4M8gQDynSDCO4NhSCxKm3xrF8c3QEhDjc3h31lfZaSt2xLwH9r52GhRbv9d6wBdMUrBN2pgbjB3ubocEQw", "name": "Whitten & Proctor Fine Art Conservation", "rating": "NA", "id": "883a8c5ef35ab28e1630235ad65a6b16506a67fa", "job_title": "Roto--rooter-Plumbing-%26-Drain-Service", "place_id": "ChIJ8YuXE6K4QIYRn1SF1hazFEw", "address": "1236 Studewood St, Houston, TX 77008, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.3858767, 29.7300997], "type": "Point"}, "properties": {"photos": [], "types": ["point_of_interest", "establishment"], "reference": "CmRSAAAAF3TSS3cVuiV18TSILVsIw2Fuzm48dEQA7JvDAuym0CN2olV-Ej0bB1vcA4IGmhEHGTqL1dKbNTcLIUGsoS4hMTsDdoowbyBRx6Jk1RIv5w0jlfPtgpkPZ5-O1Mvr0OCoEhD7rrKAqcDdueD-DlI8QiqMGhTdQnNXVkv1KTQ5RGSkkJ7Gt99a7A", "name": "St Mark Fine Arts Conservation", "rating": 5, "id": "ea2d4bac6d74716b33f456dff3aae0cc0b43cca3", "job_title": "Roto--rooter-Plumbing-%26-Drain-Service", "place_id": "ChIJKbDEoXm_QIYRcRFBlp0dE8A", "address": "4901 Main St, Houston, TX 77002, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.483218, 29.7482286], "type": "Point"}, "properties": {"photos": [], "types": ["point_of_interest", "establishment"], "reference": "CmRRAAAAxekaslYwMdeUblLkFO8Wzaw2teZ75UuRe_rcmB5MuYveU6Zmz60v1MAMRB1TXioGYpF0sNZYGQ5IJwKw3mjzvgqf-qAgheOYrN1YvNs-sZSeOC-1cHrPHrE6cgmW7M3aEhDGB88KPoQDY6Vo37WuHZojGhTFzTrr-iJN9aXBgL3NPzTScgRGpA", "name": "The Nature Conservancy", "rating": "NA", "id": "90af6fb9fb926dde9f7103577cebc4150bbb1dec", "job_title": "Roto--rooter-Plumbing-%26-Drain-Service", "place_id": "ChIJq-m4EX3AQIYRJkn4Lhccp2E", "address": "1800 Augusta Dr #240, Houston, TX 77057, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.42318089999999, 29.7345943], "type": "Point"}, "properties": {"photos": [{"width": 750, "height": 437, "html_attributions": ["<a href=\"https://maps.google.com/maps/contrib/106788706324997826205/photos\">Erika</a>"], "photo_reference": "CoQBdwAAAOLKTtf0LAPMXlZ1hOkoIfo06rwoNerVdwL1TxuXsYSWxJG9ilEwcql7zKCC5NRr9fP3veIbDrWEjr_Eya3y-BWf73rg7KmM9VyWIlBVEcNalDagwBgSuFlaXknguPXmWvTOzNJCtWZWapulhBSAYJ6Xp3w7lsznl4xXPmG3JqmkEhDritefRkPUV-nlkFXrdJYRGhS36SlOtYaVd2PnRtuMsJXQhIvf-w"}], "types": ["point_of_interest", "establishment"], "reference": "CmRRAAAAA4Nqs1oGdf8pq7Q7OxmDWL9rSh5WdUJsBsO_aYMfJY4nokfTn6SGMBaWxMppAvMUaW_xqtUi5AVzkWXy8oK0t3g9hKLp2s_toNoCnMJ6UH4hqrrlQ5-7v6qhEAdv3JIEEhCLiiSbJP1Mr9xlK3NYouJlGhSnBHp0_6ic2VgvnUkL40oblqbwrA", "name": "Student Conservation Association", "rating": "NA", "id": "1c5ea7722fc0d99e9f7dfca55f5d9078224d51d3", "job_title": "Roto--rooter-Plumbing-%26-Drain-Service", "place_id": "ChIJQcqBXfDAQIYRErawO-goGj4", "address": "2990 Richmond Ave Suite #400, Houston, TX 77098, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-96.038102, 30.055621], "type": "Point"}, "properties": {"photos": [{"width": 984, "height": 985, "html_attributions": ["<a href=\"https://maps.google.com/maps/contrib/110279808588468038448/photos\">Peckerwood Garden Conservation Foundation</a>"], "photo_reference": "CoQBdwAAAGVznqfVRbd9xRLgpfuzGB6n__CDaEW1d9vDttaVzZsHg4dG6mFmEXfxt-krxiqUlSiDvPRHkad_t_bD8riKbX2RQeCDp2Y4VuRToOElNamesUhXDkacuopxvSH8sr1on-3vaxLAjoc3GjVJsN3Kt7ai1pFrSMemYaxqJkmpPhG1EhBfE8xd_algKU6CDO4AZV_LGhSlPFqVMvcd5kec-FGXDHnQJQjWeg"}], "types": ["park", "point_of_interest", "establishment"], "reference": "CmRRAAAALzRn6BCSWQgCJRXuwFfsiJ2TJY6cXkFI7f551JCQJUod80IP1OIpWeYVzCWy_5tXZ0ZDjsYjRSr7Lc_Djj_1_8pzBOYtcfKm3NHZXmI8bvajGyo2n5FGxmo84EePmvIoEhCGlCwWkCtR360J3xk3Xg8xGhS7Pa2MCdcKdEv_IuOF3RkipcfR-A", "name": "Peckerwood Garden Conservation Foundation", "rating": "NA", "id": "e618a4c618cd67ce4f5fdc165f640220ab3b53b2", "job_title": "Roto--rooter-Plumbing-%26-Drain-Service", "place_id": "ChIJmUR7pvHKRoYRIIl0o73bPGE", "address": "20559 Fm 359 Rd, Pine Island, TX 77445, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.64386449999999, 29.7515036], "type": "Point"}, "properties": {"photos": [], "types": ["point_of_interest", "establishment"], "reference": "CmRRAAAA9OHPAXMc3YdIYdHNizdoKrdeUWewawCKOPKOhzggy1R2O-BVVzJw8brngIocn55f3uBSUA-4_Xv9ZoRIxrllRCWCM6wetkwBUuHHJlFaqLsqLBY5i3ebHAb1NWTZBN7bEhD2kOB1kA7AqROcKvEp8q0hGhR2G1GkJg9mocWZs0I9u4Cz3PV_Qw", "name": "H2O Conservation Technology", "rating": "NA", "id": "30c07988ef8dfc62dac712b9d587daa4a36f2539", "job_title": "Roto--rooter-Plumbing-%26-Drain-Service", "place_id": "ChIJIWZRKeHKQIYRXxta3wOMGGc", "address": "1725 Hwy 6, Houston, TX 77077, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.5705632, 29.7714443], "type": "Point"}, "properties": {"photos": [{"width": 3024, "height": 4032, "html_attributions": ["<a href=\"https://maps.google.com/maps/contrib/108143329814504597326/photos\">State from Jake farm</a>"], "photo_reference": "CoQBdwAAADD7lmS6iluzmCnYhLl_Qj2vxQ6JM9E7jWT_n1cxHm8ge3MskIMSr9vKqeNms6tyutRNjdp-DSbIoNHZGKraHe3Ko2nw1JwAY1jTeo6v-ugZyTuB5dn67S2rPWqoQzNjgYzV3S5Nc6faplmTh0gBnyRLrwOWbSgyzjTRlJ2mSCdAEhDaz9WWNf16XhdsHofUySpkGhQnUgGW-4LDHbxTGkMWN9yc8NiHrw"}], "types": ["park", "point_of_interest", "establishment"], "reference": "CmRSAAAAsTdPHgKxmmbkSX14NVJm2fM5EalLTOtiajoMPJyKhS40DRMS7W6LgHox2EzEBVzSa9MUpFK9lEunjGARBxIj-lATmWkyY9QFcTXcZ2mbb1DS47j5wuzgvhPfcdA3W2AeEhBJfoxZWbLeqxj8VLM-730tGhRRAguDDF-wwhKdDdhtWhefUwzPAg", "name": "Houston Audubon Society", "rating": 5, "id": "050a5458d86bdd1cee7b09678bd6256d0a20a73e", "job_title": "Roto--rooter-Plumbing-%26-Drain-Service", "place_id": "ChIJlQOxwVDbQIYR2uX_TZl0TYc", "address": "440 Wilchester Blvd, Houston, TX 77079, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.56820189999999, 29.770778], "type": "Point"}, "properties": {"photos": [{"width": 1800, "height": 1200, "html_attributions": ["<a href=\"https://maps.google.com/maps/contrib/108765250995932379967/photos\">Audubon Docent Guild</a>"], "photo_reference": "CoQBdwAAAFywpdp8bVWxigDxV_p3d56UkjiEdE-vVUzkRFLGduOOvifH_rDTwo3UkLwgxEv3T7lLe3FEnVS5gq7Lwtl8xcJPWxUP87c_RuPn1NRhhvhTvZ2e-XKtyqvhLMNLdnfmVjX4E4AlNuPVpRHV1LfX0ej_R--xUJd3YMNPwoh4LdQOEhBWezaaySSSPZhz01CJoBk4GhQKtSKStAI-Jk81hu0YMI0yRXgU-A"}], "types": ["park", "point_of_interest", "establishment"], "reference": "CmRSAAAABxAp_vXXik6DmLM6LCSfp0x5QcHxzAhMLtEzBA3JY7AbuS72jke4OY0pEZNW1UbdNewDFdfoOKY_nlekRWhw-F7QobBn6hjZ9-4sNoYa_vc7zI6DL5OvORTOkAVFef4PEhCaHAYY9scj7-pSgG6e-QwjGhR5bWut2UMsKovWBtPS3cxL6PKqaQ", "name": "Audubon Docent Guild", "rating": 5, "id": "7ddd5daf76cc4979e2ba6b062322d1c77d5d1c07", "job_title": "Roto--rooter-Plumbing-%26-Drain-Service", "place_id": "ChIJI9XyNFHbQIYRtwHb8EtTpeU", "address": "440 Wilchester Blvd, Houston, TX 77079, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.44932349999999, 29.7803218], "type": "Point"}, "properties": {"photos": [], "types": ["point_of_interest", "establishment"], "reference": "CmRSAAAAUGdar2pf9pQYf2JYhV2ATPshBgcHnB-2Yu7xZgcPeSiR9JkLNXBRd5PoisJfcagAepcUltVpuC0QU7n1HJn6LwhSaX1OWMnrFo7_EroZFBmC6P5UC9D0iDkZ0-jb54ZcEhBOp8LvPPtvwYl5_1s6s6KKGhT6DRfcT65CGbhYaVTyruMC0sR30A", "name": "Coastal Conservation Association-Tx", "rating": 3, "id": "7258b034e119f31e82320bca6e72781ee9f79d75", "job_title": "Latham-%26-Watkins-LLP", "place_id": "ChIJcekacM_GQIYRPzL13cgQrPk", "address": "6919 Portwest Dr #100, Houston, TX 77024, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.47039, 29.655454], "type": "Point"}, "properties": {"photos": [{"width": 5312, "height": 2988, "html_attributions": ["<a href=\"https://maps.google.com/maps/contrib/101184977609161362375/photos\">aug4</a>"], "photo_reference": "CoQBdwAAALcwevqbumMGd5Rd-bOodRIENR8L8kzI02buh9J-v-ZvfKd2dbdZaDbekU65oSp8HfOJ8jJuTtiFSBrBJfuIJWiZPh_aZkq2F_aPjS6BVnMr7Zx5wBzgCDe64lNcGxK1PYI7DR5Mjn3TL94P3Z9gzXZVFZPAi6XTGwU0oQ6xMrySEhBEE51Xc30hV7IWCOsA09BFGhRPczfAno6mpYLnuwBkD5WyI4X0Jw"}], "types": ["park", "point_of_interest", "establishment"], "reference": "CmRRAAAAIMSZwNjC0tpEkO-xMe7dI4S9SIvUJ3P9BCZTC64vDjWwPyHvt-notU4Jqn7c3WgAybj4D63qKJbJ4h8vWF_HkPkP77NlDA4Zki8wOIf20c6lVDdYtDVfl22xtSnwu5iSEhCd7cfudepJoCGqzTiDeIUMGhRViWHwUqI1-ZCm-l0XikXflk4E4Q", "name": "Willow Waterhole Greenspace", "rating": 4.3, "id": "0127506e8071350c2d48f0ca56e939045297a0f4", "job_title": "Latham-%26-Watkins-LLP", "place_id": "ChIJR6_2zTzqQIYRsA7wExgfDWs", "address": "S Willow Dr, Houston, TX 77035, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.4003322, 29.7388505], "type": "Point"}, "properties": {"photos": [{"width": 1136, "height": 640, "html_attributions": ["<a href=\"https://maps.google.com/maps/contrib/117056878997299689379/photos\">Marisol Brown</a>"], "photo_reference": "CoQBdwAAAE7MWaZYwA8Rnl06yT_IC4d7ZMRh2zFPCJccq6hXEsLEI5VwIkjFMXMV2Y-k0r1xzLlk85_ju_xZjSEEk98KyJMWZ0W8SfZj5ZR6nu4YzNrfJQGoXYBRIdDpMy-kMHd4M2vSgk6xIC4lNFb-buObiOCl1lPnCZuqSK2St4A42UDOEhDt6T1-c6pvuaW6gCFs7V8jGhSDhZQfyZlhRhLf9v3bfZINwEcrcw"}], "types": ["point_of_interest", "establishment"], "reference": "CmRRAAAAWMml7glLHQnGBjFqDNG2b1MA0sTFgaawrLzTwketYashIrUGQzSqCkbSrGD-JQfgbiw5sUlDlSbGFHW49XamuZSrboyFK-EitxWot-CxmXMiebjaYOIMi3SOd5DyQLu8EhD4nR9mu-beOOQ9b5EvlFbUGhRDVNMxDhMq1T0AGt7yw2N2qfdLbg", "name": "Masters Fine Art Conservation", "rating": 5, "id": "a462c2eef4e22ea319485ae7b84f3d20756cbdd1", "job_title": "Latham-%26-Watkins-LLP", "place_id": "ChIJp8u2bZvAQIYRbosnWz6cVmY", "address": "1612 W Alabama St, Houston, TX 77006, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.3876169, 29.794149], "type": "Point"}, "properties": {"photos": [], "types": ["art_gallery", "point_of_interest", "establishment"], "reference": "CmRRAAAAMXnBOo0JXr6gV_wAcQQzTO8mkfhdguG8GroQSjJcOOjTzjSpULkGRDv-z1TNDMkjrRHg4TpVYsPn6CaagpmA2KXg0WdIbgl0_3LztjsitdhQVcVw9KHf8dT4lM1PThkgEhCjeNpdq0S2L651lWrvgW3-GhSYnth3YJEVwKGHcUpS2suqPEssmw", "name": "Whitten & Proctor Fine Art Conservation", "rating": "NA", "id": "883a8c5ef35ab28e1630235ad65a6b16506a67fa", "job_title": "Latham-%26-Watkins-LLP", "place_id": "ChIJ8YuXE6K4QIYRn1SF1hazFEw", "address": "1236 Studewood St, Houston, TX 77008, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.3858767, 29.7300997], "type": "Point"}, "properties": {"photos": [], "types": ["point_of_interest", "establishment"], "reference": "CmRSAAAAvGMQU2gc7pBh22riynMHM9SEvNJpPyrvDqTHNSinjVyU6P8bTXrN5S4pPiisxma8IZR_d0x2kKCIBqFovQPIf93G2CsFBmB9ofS4ul29Hh1G3OAiYXzo_RYY-ob5XjeREhBvwKY3tmU6jzCuk33XzvIoGhTIaPnBp1HhWQr_juSvZENNmlMuPw", "name": "St Mark Fine Arts Conservation", "rating": 5, "id": "ea2d4bac6d74716b33f456dff3aae0cc0b43cca3", "job_title": "Latham-%26-Watkins-LLP", "place_id": "ChIJKbDEoXm_QIYRcRFBlp0dE8A", "address": "4901 Main St, Houston, TX 77002, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.483218, 29.7482286], "type": "Point"}, "properties": {"photos": [], "types": ["point_of_interest", "establishment"], "reference": "CmRRAAAAzdE85dIyzZzXp5oYpV32Q_gOb3Qrj3H-Z9wWzS_HiFAuApU3vyNPRJVw-qMqvfsoGeWe0HrAD3Ng2RFZmEqk2z3TT7X04FPRs1hT9eSouGZQ-2rdPn6QXkeZR4uasqpNEhCp9M1DOzGnvoMdGOVjub5rGhSRDTZP-r-8x8SzMrS3ZUhXmyZDvA", "name": "The Nature Conservancy", "rating": "NA", "id": "90af6fb9fb926dde9f7103577cebc4150bbb1dec", "job_title": "Latham-%26-Watkins-LLP", "place_id": "ChIJq-m4EX3AQIYRJkn4Lhccp2E", "address": "1800 Augusta Dr #240, Houston, TX 77057, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.42318089999999, 29.7345943], "type": "Point"}, "properties": {"photos": [{"width": 750, "height": 437, "html_attributions": ["<a href=\"https://maps.google.com/maps/contrib/106788706324997826205/photos\">Erika</a>"], "photo_reference": "CoQBdwAAAN_fFuK5-IuaBDxPbm4dCyUDnT1mpKsFs1GvL_Td4mGarf-ckAUgooYdrDVszVOktCKAtSmDjIwdbmZaXDNHlvT0oWgvHIkHJbVCGHlIzoBwbqhWFvki1AWm8Q0u-0XS5vqiUUfYT7W0EaB-6RjvHuFVEaO296O3_Ve4n6SsEiXyEhCU7ChDv30hj4Z_RImMRm9LGhTqAbPdk75-AGFh5k7_DzDcMjf65g"}], "types": ["point_of_interest", "establishment"], "reference": "CmRRAAAA8GTWDtJ77eU32VY1H0xStjxLSF4oKVRoRLtZT5Wh6CDBJPsP_ve10xpe0etaONetLzo2snX2vyl8Y_r8OxGPQYJWYMF-eO94mbDfz3pNB4lwa26EftXBRUlU5mywNPUNEhA1wOboQ-xCPt7IiiYt9fi9GhRjyvNHodu5q2Ynmfk9U4j3wmn6vw", "name": "Student Conservation Association", "rating": "NA", "id": "1c5ea7722fc0d99e9f7dfca55f5d9078224d51d3", "job_title": "Latham-%26-Watkins-LLP", "place_id": "ChIJQcqBXfDAQIYRErawO-goGj4", "address": "2990 Richmond Ave Suite #400, Houston, TX 77098, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-96.038102, 30.055621], "type": "Point"}, "properties": {"photos": [{"width": 984, "height": 985, "html_attributions": ["<a href=\"https://maps.google.com/maps/contrib/110279808588468038448/photos\">Peckerwood Garden Conservation Foundation</a>"], "photo_reference": "CoQBdwAAAEiQ2HxeXfy8EnDBsPAgYT5Bha34KUNdXzieYbTZagNOFPlLEG_iE_cZsF58VgaFISdq_SBcyg_o2Eiifb1Ym2QMKEQ2AiUkrlNTOD3aYeH0-9TOSinhKBNVhiHm3bKrcpsP-8rj7jNk7mEzlz0jH5k8quiBUSzsIrGRRQMdNJ3TEhDXGnrIk2OYKhYUuIQ9KByAGhRsQpo5C4Xl2A3itfx0uIpdridu8Q"}], "types": ["park", "point_of_interest", "establishment"], "reference": "CmRRAAAAREOm-quYCJI9FiUrUw7FaH7uknaIx7zJEQBY1w_qm01t0H9jyNCeddG-M_9MrkEPP1NDVIrnemLOe3Ul-ItAdG0fyjpRGpT0cVXr75m6IzR8Z714T7UZBb2jQ5OKxXayEhD4UuJ1xId_G8crKT1JyE2YGhSLwClJeTjix9buu7j3Ko1n85TtnA", "name": "Peckerwood Garden Conservation Foundation", "rating": "NA", "id": "e618a4c618cd67ce4f5fdc165f640220ab3b53b2", "job_title": "Latham-%26-Watkins-LLP", "place_id": "ChIJmUR7pvHKRoYRIIl0o73bPGE", "address": "20559 Fm 359 Rd, Pine Island, TX 77445, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.64386449999999, 29.7515036], "type": "Point"}, "properties": {"photos": [], "types": ["point_of_interest", "establishment"], "reference": "CmRRAAAAgStT3dTL30_66Q02WxexWu6mGSd3K_GH8F8bBgTgn6lDhesKwoyQoj5_7AURMFULahUjJTf3ShWEsRMuO1JjlFPvZeEkEiyiRV72QQ7HYJ29xek4trqw9jL7HfTAWyOGEhCAkrXfrNjnQvsV1SCyKs8kGhRInVOi5g-l1dmQA0mCDKmrI89e3Q", "name": "H2O Conservation Technology", "rating": "NA", "id": "30c07988ef8dfc62dac712b9d587daa4a36f2539", "job_title": "Latham-%26-Watkins-LLP", "place_id": "ChIJIWZRKeHKQIYRXxta3wOMGGc", "address": "1725 Hwy 6, Houston, TX 77077, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.5705632, 29.7714443], "type": "Point"}, "properties": {"photos": [{"width": 3024, "height": 4032, "html_attributions": ["<a href=\"https://maps.google.com/maps/contrib/108143329814504597326/photos\">State from Jake farm</a>"], "photo_reference": "CoQBdwAAAJ3gvfjCL6rGgj84UZ1vWNN4cVmboiovp1iOFotkpo7pLTUntEdEObd5vpELhNi0pt8c-TdG2ckaHIbaUUgXb42YCkCy7XX1L2aTXvHBpBzfiueCY3OejjVCdWSytrct28lNYu3h8HYUdnif0mcXl3eWJQOnlOKFchM2rOxWt5iQEhDb-oOp8T8WxrglkGffDnzZGhRDKW_7Odci28xReQd3STOCen1RGA"}], "types": ["park", "point_of_interest", "establishment"], "reference": "CmRSAAAA3-95gPvYM0oX9rUTXrvv7vK0P03taYMv4E0uzbT3dbx9zW-DEKBlV3Yt18Y_lbnuO60z_NQMbupoFtwKdogmItWYZsgoOSK5IVxeLny9dHh_aw583SXpCZ_g02vMzOYlEhB_HcZgV6o9tBuU-Dhbt2a7GhTDN76CIjwy643eYd6Ce-ZjJyfM1A", "name": "Houston Audubon Society", "rating": 5, "id": "050a5458d86bdd1cee7b09678bd6256d0a20a73e", "job_title": "Latham-%26-Watkins-LLP", "place_id": "ChIJlQOxwVDbQIYR2uX_TZl0TYc", "address": "440 Wilchester Blvd, Houston, TX 77079, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.56820189999999, 29.770778], "type": "Point"}, "properties": {"photos": [{"width": 1800, "height": 1200, "html_attributions": ["<a href=\"https://maps.google.com/maps/contrib/108765250995932379967/photos\">Audubon Docent Guild</a>"], "photo_reference": "CoQBdwAAAIRfHf3Y2AkfJALsue0D45uIITQHndtrEc_oWlV0XaXSvQ4MZO3YACYytwVIqfjpLfZAHyAuFvsKQMFRpUcEvZcvuEz9m38p_sZhq_HRFgi1qPXBsa4LlARXd7uTZdwYLrHxbliExFb4h_sAhZ4-ujG4azx_dkn2YGT4rXygFQfCEhDTFE0gOaKvnMUMKC_M6WKkGhSARJ1iNTmvF5ytnD7ovo4ktdHJDA"}], "types": ["park", "point_of_interest", "establishment"], "reference": "CmRSAAAAA3pSC_KVY95jurrivR1yGPSRaI39oezoueV5VeNMb_lcPHpxAnsgo9Fp75DjxEL5fE-yNIBAnuBPpHuFh3KpkD8lLemrgNTEnQ-2a_Xz7gkJcDE98cef0a_zt1sY26ZAEhB5HjRrKa1b1Qt9B_ezi5K7GhTKdhjpq1tpn32IvsPv2U2iwnUcLA", "name": "Audubon Docent Guild", "rating": 5, "id": "7ddd5daf76cc4979e2ba6b062322d1c77d5d1c07", "job_title": "Latham-%26-Watkins-LLP", "place_id": "ChIJI9XyNFHbQIYRtwHb8EtTpeU", "address": "440 Wilchester Blvd, Houston, TX 77079, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.44932349999999, 29.7803218], "type": "Point"}, "properties": {"photos": [], "types": ["point_of_interest", "establishment"], "reference": "CmRSAAAASkiq_O4_v3N4zPNuzpFK-3bETV4ti5InRWf6bix_3Vzfgu3jKQHA0JXkul8TMY2XXHORgmTp_A218xw4Oy83J_k0SXuL_2mpTutLQ0l5uZ-zifX_6LCRGh_-Ct5Cw-l2EhBFIpSX4K9gFz4QpUvQKDX4GhTPQGJPyvmVDBZ-WBPBM9IBS763JA", "name": "Coastal Conservation Association-Tx", "rating": 3, "id": "7258b034e119f31e82320bca6e72781ee9f79d75", "job_title": "Ut-Health-Science-Center-At-Houston", "place_id": "ChIJcekacM_GQIYRPzL13cgQrPk", "address": "6919 Portwest Dr #100, Houston, TX 77024, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.47039, 29.655454], "type": "Point"}, "properties": {"photos": [{"width": 5312, "height": 2988, "html_attributions": ["<a href=\"https://maps.google.com/maps/contrib/101184977609161362375/photos\">aug4</a>"], "photo_reference": "CoQBdwAAAMiNpfsKkY1iB3G7TQQ24Ans3mdUwt8T9tRayWHHtpLwyTUSJMXlpLr4en8SHXkDquR2qhEVE_er-LLnNBWF87cHtOlprq7PlbyQnIVpxNt9zDMTdMkCppm4gdVWt8X2D2y_Bg7gWNhJJDGqsNUnpsTxWJhPPlJ4eJbqbcJnWvCNEhCEBOpHThoRScdRe1KoZzi1GhQkcCYTuJGbnQXDXHsnVi0L6q5BIA"}], "types": ["park", "point_of_interest", "establishment"], "reference": "CmRRAAAAs15GqkG9kmtTbiDH6dAtWXx7tbOT9EgQwcF2EbyJacrZOQDMbakZeQQR9s1mRN-xp8iq_pLrFTE44TT1qMWjBqZPa1-liZRRTz3KJXobPDU7EEOwBRrFB7K83wGFIaXhEhDceAAStonHAlqq_27mJpkEGhTeMIWmQfvYSSLxQMUQePpVbhhDRA", "name": "Willow Waterhole Greenspace", "rating": 4.3, "id": "0127506e8071350c2d48f0ca56e939045297a0f4", "job_title": "Ut-Health-Science-Center-At-Houston", "place_id": "ChIJR6_2zTzqQIYRsA7wExgfDWs", "address": "S Willow Dr, Houston, TX 77035, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.4003322, 29.7388505], "type": "Point"}, "properties": {"photos": [{"width": 1136, "height": 640, "html_attributions": ["<a href=\"https://maps.google.com/maps/contrib/117056878997299689379/photos\">Marisol Brown</a>"], "photo_reference": "CoQBdwAAABpB0t3jvdw2gKNVwdKdu05yNptiW08x57cA7wmVGNb-qZMrZK-nNQUwtbrBFI3XAVbYWCFB2eWs2owxZ67F9ZQoKc1IaVYAKSbFntm4Hhd-3m1d_PRL_f0uVY4GuXhlunUMc2OFCwNqryaulM9YcD5Ybk-DcUddwSU6wG_6w9qaEhBXZ4upavkL_FWqpSjv0g-8GhTDqnm6ZQ_RQEl35knCvhq5z19IOw"}], "types": ["point_of_interest", "establishment"], "reference": "CmRRAAAA14OZI4BqMX2m-qntMDxmpHYTAD2N87uXSz9CNE-AAKvz0ujBFbm2vwhTkqoZ4vv0lwwMBCUM29AtSZcnTGN__w_8s0_DcAuoJDBaJn4jPWBhllQETX6z9VOmzsiUqIgCEhDD2PV7Wlg5MyrjVulrUUkeGhQ63eBi0mQQpDFsd-Kh5UofLhYZhw", "name": "Masters Fine Art Conservation", "rating": 5, "id": "a462c2eef4e22ea319485ae7b84f3d20756cbdd1", "job_title": "Ut-Health-Science-Center-At-Houston", "place_id": "ChIJp8u2bZvAQIYRbosnWz6cVmY", "address": "1612 W Alabama St, Houston, TX 77006, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.3876169, 29.794149], "type": "Point"}, "properties": {"photos": [], "types": ["art_gallery", "point_of_interest", "establishment"], "reference": "CmRRAAAAlQJ3Sc_2qgyc9sLSm2JAQft-bYu5Nl2WJT3M3liWYH7BsqqQOqd5I2WoUC9AXW4SErFjJC2knnfokIqmyqR6fWOtACGtukSQF5-Bs4GRCQQdlPjiu86lLlpQ1x44t-RMEhAYPPkq6KprIA8ZTj_1SrQ4GhT4aPXk83T53-X7ae_lHKr7iYMNIQ", "name": "Whitten & Proctor Fine Art Conservation", "rating": "NA", "id": "883a8c5ef35ab28e1630235ad65a6b16506a67fa", "job_title": "Ut-Health-Science-Center-At-Houston", "place_id": "ChIJ8YuXE6K4QIYRn1SF1hazFEw", "address": "1236 Studewood St, Houston, TX 77008, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.3858767, 29.7300997], "type": "Point"}, "properties": {"photos": [], "types": ["point_of_interest", "establishment"], "reference": "CmRSAAAAc9oHa0LlOwKW-LM94nj777qdvrkGxzhAyxDp1J5fTf76_SR9aaQk81tuFR_iCxRXqr1AtJJj-tmlktgtJN09e3XfnWaczRC50untIbYiM9ia9iVKfi4LHzgCICWr0O_qEhDVdsuIHVi25agZH-lYJkxfGhR0BgWkIja5gtkEdkbh08bioVJowA", "name": "St Mark Fine Arts Conservation", "rating": 5, "id": "ea2d4bac6d74716b33f456dff3aae0cc0b43cca3", "job_title": "Ut-Health-Science-Center-At-Houston", "place_id": "ChIJKbDEoXm_QIYRcRFBlp0dE8A", "address": "4901 Main St, Houston, TX 77002, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.483218, 29.7482286], "type": "Point"}, "properties": {"photos": [], "types": ["point_of_interest", "establishment"], "reference": "CmRRAAAAscJeW-j8Q821wXUHS74ZggR8qOdhUQmrKF7O6cRtWnDwiniia3xIMavUQlOWfaOMI2-btsJ6BNxlkB5SCLQWYEp88ziYGL3YgPvfL95Zcenp_JvTFUNddKoku-iOv4unEhAvbwTqHTk-W_wuw0PculFGGhRR1Si_EypU2sGJyM3GwmjHzRaz3w", "name": "The Nature Conservancy", "rating": "NA", "id": "90af6fb9fb926dde9f7103577cebc4150bbb1dec", "job_title": "Ut-Health-Science-Center-At-Houston", "place_id": "ChIJq-m4EX3AQIYRJkn4Lhccp2E", "address": "1800 Augusta Dr #240, Houston, TX 77057, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.42318089999999, 29.7345943], "type": "Point"}, "properties": {"photos": [{"width": 750, "height": 437, "html_attributions": ["<a href=\"https://maps.google.com/maps/contrib/106788706324997826205/photos\">Erika</a>"], "photo_reference": "CoQBdwAAAD4VITijCY-HpDyN33lXZIzTNfvo9wMiEsKPLAZUwtQFwscwhcAWU0fpd9AT5XH-Y0Swtx60YcU6a_6jGvR2U6TAgRWL8td0yoNK1RJNXskYHel7imxqPXdLtyACQNf9d8QGi--QkbUPj-uaLm81Jn3VDEX3MWEsBzsXFMBzm1LeEhBO_bzfQn6zHdjGH8l796yaGhQvxhbJOV5Qh5j4pA0RYrYHT6qAqg"}], "types": ["point_of_interest", "establishment"], "reference": "CmRRAAAAZPFpf2-4qbkDaU_OJARzluLL1Kmg1OSo1C3qpE4K84eoz97pBIBOqrHZ2_H6_i5icJBer3YE8hs9QbEVBw-l73UUCVtkSmzcyXWFhh6HW3yCCsLbKowUJVjZVit3pr-uEhCipdPrK1wY_3_2ZeR72YHPGhSVdjcFtWz6Os0Pa53chpxHO4JZuA", "name": "Student Conservation Association", "rating": "NA", "id": "1c5ea7722fc0d99e9f7dfca55f5d9078224d51d3", "job_title": "Ut-Health-Science-Center-At-Houston", "place_id": "ChIJQcqBXfDAQIYRErawO-goGj4", "address": "2990 Richmond Ave Suite #400, Houston, TX 77098, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-96.038102, 30.055621], "type": "Point"}, "properties": {"photos": [{"width": 984, "height": 985, "html_attributions": ["<a href=\"https://maps.google.com/maps/contrib/110279808588468038448/photos\">Peckerwood Garden Conservation Foundation</a>"], "photo_reference": "CoQBdwAAAI8XgCfiwypTIKF7Vc_FH_R-4CF-vAalBDNhTWlXCIhbUCAv9fatRj9jDbameVYJQRyEFQxs68TAYvAQmOExXzaPSE13-6SsMNgcMWluqSX-8AY68Ngt2KGf5USYxr4iVMpBs-guU4xNzFd6NqPluFLXQwfFax9x0W3T50NVabUgEhDEnhXfQYZUl6IBGkTZ2O6XGhSNEEsOWYRTkGMHMf2hvO7tVjW7KA"}], "types": ["park", "point_of_interest", "establishment"], "reference": "CmRRAAAA8F9Ejv5nCLWkmfbc_NCDi6CPFn2kZtC88tYAJ7XxIoQzgSGlD7rSnBO6Kh9DNuyK8vLUqLNJLFkLI_4ytuspMQ0fYKM2HtxpLsgQjjwyNnk2SW-Sp8PGrdHSklmIV3JdEhB26AcMDp4KhlXUg1S1HBlcGhSO88h58gPb_P_IpeSqhKUO4OhGTw", "name": "Peckerwood Garden Conservation Foundation", "rating": "NA", "id": "e618a4c618cd67ce4f5fdc165f640220ab3b53b2", "job_title": "Ut-Health-Science-Center-At-Houston", "place_id": "ChIJmUR7pvHKRoYRIIl0o73bPGE", "address": "20559 Fm 359 Rd, Pine Island, TX 77445, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.64386449999999, 29.7515036], "type": "Point"}, "properties": {"photos": [], "types": ["point_of_interest", "establishment"], "reference": "CmRRAAAAqpkI2oiME-6cz7puVTLFoIpBIgRQA4T-hnnCtf2P8o7CpKpQe7VNhyrdvsC5zwIa6YLLeMNKlJVT37J0Jqd8h_pVGEI8cGbKwCs55xmdF3sp0pzFX1SGTjXZhxauvSoUEhBrUc_C2LV_FVLPW1KEAWXEGhQ4H_IrwQ0-4jwyFc49Z6rHWa-Lag", "name": "H2O Conservation Technology", "rating": "NA", "id": "30c07988ef8dfc62dac712b9d587daa4a36f2539", "job_title": "Ut-Health-Science-Center-At-Houston", "place_id": "ChIJIWZRKeHKQIYRXxta3wOMGGc", "address": "1725 Hwy 6, Houston, TX 77077, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.5705632, 29.7714443], "type": "Point"}, "properties": {"photos": [{"width": 3024, "height": 4032, "html_attributions": ["<a href=\"https://maps.google.com/maps/contrib/108143329814504597326/photos\">State from Jake farm</a>"], "photo_reference": "CoQBdwAAAJmiCJcSQdykWLBJGWy1N49jFjGMkNW81rEGENl89UwIKDt5INxUcYifIXsBwDJAl7F6DSoX0pZ3qHVP45XR6vVAKVsMuK-1yhBuB-xjp-IiSm6CCbiD4vtlHEhDyhoJWfP8NNWwgfLK8lFM0jdIxB43_GZ1wQ4uUQA7bUdv_dROEhA2Ue742CQNwquIsya_TytOGhRdpPV-Z_3ps8kdluLD5bfhyqmrhQ"}], "types": ["park", "point_of_interest", "establishment"], "reference": "CmRSAAAA_THyJ4Tl67LqV_0kxqnAb4DUP-NRrSP9Q9mbvqJSzO6Vh13GMpdh5_zHBEpZk8cPsDRydCYTX5aGVl8A9w9TM9gPaXJZEiSHrfl66gsbLiut-YJOHUN6Abvd_w3kBA5uEhCIqFqNKHyNRQxc2kaw6FldGhSAU4rxsMHmk8P1ZNbC0_2WKNT6yw", "name": "Houston Audubon Society", "rating": 5, "id": "050a5458d86bdd1cee7b09678bd6256d0a20a73e", "job_title": "Ut-Health-Science-Center-At-Houston", "place_id": "ChIJlQOxwVDbQIYR2uX_TZl0TYc", "address": "440 Wilchester Blvd, Houston, TX 77079, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.56820189999999, 29.770778], "type": "Point"}, "properties": {"photos": [{"width": 1800, "height": 1200, "html_attributions": ["<a href=\"https://maps.google.com/maps/contrib/108765250995932379967/photos\">Audubon Docent Guild</a>"], "photo_reference": "CoQBdwAAAAKhOtSt34Wc7qJdjtoWX0qqG2dJbEWt2h4vQcjuldtVl33OIcFWqhlAF3cqdIggxs2u3zOz8XX1-zCXfN_UwN667VasMyinWjSrI6D5jAQnn8W0yepjojDZpXe2oeA1F2YDlW31l0dWXdyNrPwFaQjjowkbScUvjF_43Yvn3xWMEhDD9wPP9nxTpNOSuNN9aaU_GhRWJ72F86cyqRgerXNVuK1x_SDb1A"}], "types": ["park", "point_of_interest", "establishment"], "reference": "CmRSAAAA6_iO1R2VDp7rDUDs6eVAejX1lzWSGiddOLUjicY6qZ2aTFv8lK_vMbiogs49n02QNqH8whY1eWL-uGNlI00BgJg3g-tNfkYn3-pjnGcItqMWXe6sDb9RJgLtZvuWascvEhDzVxOsR5jRggH2qpIKTlA9GhSDdkFXMeQmWDMg3UP0Uqgz4gBdmA", "name": "Audubon Docent Guild", "rating": 5, "id": "7ddd5daf76cc4979e2ba6b062322d1c77d5d1c07", "job_title": "Ut-Health-Science-Center-At-Houston", "place_id": "ChIJI9XyNFHbQIYRtwHb8EtTpeU", "address": "440 Wilchester Blvd, Houston, TX 77079, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.44932349999999, 29.7803218], "type": "Point"}, "properties": {"photos": [], "types": ["point_of_interest", "establishment"], "reference": "CmRSAAAAcI3VbFa6iv7-MXw0zAtcp1v6cOP6FRTJ6_QbpMuo86J00uKiMeTaebba38BzGTdxkTHR-x_gBD6LdgpgmhT5gaLR23Th2UKuyx0rejGViUoNqcwMWJOdl8J0Oy8_SjjWEhCHekIQ6J4I5UC1p-G_CuhRGhRbOpRErEVfpB3g22nlOrd8KHzO6g", "name": "Coastal Conservation Association-Tx", "rating": 3, "id": "7258b034e119f31e82320bca6e72781ee9f79d75", "job_title": "Contemporary-Services-Corporation", "place_id": "ChIJcekacM_GQIYRPzL13cgQrPk", "address": "6919 Portwest Dr #100, Houston, TX 77024, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.47039, 29.655454], "type": "Point"}, "properties": {"photos": [{"width": 5312, "height": 2988, "html_attributions": ["<a href=\"https://maps.google.com/maps/contrib/101184977609161362375/photos\">aug4</a>"], "photo_reference": "CoQBdwAAAGrjtURHwplGNfSRZBdHyT9lzzPTVvhrhx2dTMJ0vQba8nmoWWm2Mm0yld6MeMzIdnT1TxwMGN6vnbJ0tRJzo0F3S5LbPvE1OXwuInlL8ZxDD7Diwhhz8201i9GGeT8PezV0EJow6N5S948rPv3iCQI0bD0_6zt8Z1lR43uyQInoEhAYFZ3u9nQOFojE0zATK72YGhQQHSzmTZxSkqwQy5LVBYjs6Z4lLw"}], "types": ["park", "point_of_interest", "establishment"], "reference": "CmRRAAAAH4EuIS810wAGIvIwAFxGxJ_kuizI9aMZYPilwX3DXTpfAS4A3RtiCRdxCP-fOeLP-wW8vprjfkaLSTJioYYVjkGgATPBUU9O2y2_w0IAjl_ym9AnzHllxwi1JUnMZlnpEhB0PAUK73NUgD49QIILKBFjGhTw2q4OyjM-53VEXkYjGHSnRsD7rQ", "name": "Willow Waterhole Greenspace", "rating": 4.3, "id": "0127506e8071350c2d48f0ca56e939045297a0f4", "job_title": "Contemporary-Services-Corporation", "place_id": "ChIJR6_2zTzqQIYRsA7wExgfDWs", "address": "S Willow Dr, Houston, TX 77035, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.4003322, 29.7388505], "type": "Point"}, "properties": {"photos": [{"width": 1136, "height": 640, "html_attributions": ["<a href=\"https://maps.google.com/maps/contrib/117056878997299689379/photos\">Marisol Brown</a>"], "photo_reference": "CoQBdwAAAArEdVD9GPjd5vXWX4wsi065UV_uXVCm2HcMMLurTX2EgEjPl_nA36nDIriJlkoSrEXnspgT4KBpk0VsrExETkfci7TpgQz4xj_0r0nKtauVo3YThlwUnNGvOTtNL3utj8U3S9uPYSCISNjX6i9LKESBTqok0yQCQL3oH9eXchoCEhB21g3MgN7rAb_jrQNdiVtQGhS3otOBwMH8A4EXoQc2cPEXrIsaOg"}], "types": ["point_of_interest", "establishment"], "reference": "CmRRAAAAoNoFcN2aviN3cJbEbOfFKi_nccsK11i3fxU7oQ_9JgeOz1E4lj5FE2Bq5pvKMQa9y9fehbP11-jHdKLKB3BUj1pf44vNlsmKi_Uri7_AyZnP_Be3O_5ThEgDzVZmlreXEhDslPimavh_GPzQflCd09UcGhSjUjV1GA2BdiPkovRfhqtBX4VX7w", "name": "Masters Fine Art Conservation", "rating": 5, "id": "a462c2eef4e22ea319485ae7b84f3d20756cbdd1", "job_title": "Contemporary-Services-Corporation", "place_id": "ChIJp8u2bZvAQIYRbosnWz6cVmY", "address": "1612 W Alabama St, Houston, TX 77006, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.3876169, 29.794149], "type": "Point"}, "properties": {"photos": [], "types": ["art_gallery", "point_of_interest", "establishment"], "reference": "CmRRAAAAN-TKXKp6HSMathGQkyRp4cXfJR2VQFwcJvPAE42hMRXPaJHwhv2gdKArfkN6AkoJIB_wr83Wcby7Hd3Zmch22FTn4tnoUlpw3vYXa7y8Ohy_O1Rg6Ea2zAoH9qMqLG3SEhAAEgdRNrLLqMmh71jxqp9eGhTIfS0wpXMWe_8OkKd5SOH3dRbjnA", "name": "Whitten & Proctor Fine Art Conservation", "rating": "NA", "id": "883a8c5ef35ab28e1630235ad65a6b16506a67fa", "job_title": "Contemporary-Services-Corporation", "place_id": "ChIJ8YuXE6K4QIYRn1SF1hazFEw", "address": "1236 Studewood St, Houston, TX 77008, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.3858767, 29.7300997], "type": "Point"}, "properties": {"photos": [], "types": ["point_of_interest", "establishment"], "reference": "CmRSAAAAA9fL12MbAg1xY9fy39X0-Ybh_2omZkXqX4pKfdqXyZCmmIuIMDpUq9mXrkpdFcFjEJYSo4fXr9tmUY2AoeOvT5cHHOAfQ8jwppKuX1be0oJo49434jKEBvcR7d0UIMmOEhD5ww_7jcA3GPpOGWREbJ1FGhRugSS1WD2HQ-jWRO_1FD0Rqex0uw", "name": "St Mark Fine Arts Conservation", "rating": 5, "id": "ea2d4bac6d74716b33f456dff3aae0cc0b43cca3", "job_title": "Contemporary-Services-Corporation", "place_id": "ChIJKbDEoXm_QIYRcRFBlp0dE8A", "address": "4901 Main St, Houston, TX 77002, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.483218, 29.7482286], "type": "Point"}, "properties": {"photos": [], "types": ["point_of_interest", "establishment"], "reference": "CmRRAAAABh9jPeIgIBA-NOH8agglYioVsHdo_1-ga4J3R9Iw8HDTHJ4okI0R0I8sH0w1RknaWnbnp8nMK3w0lKMpNxgYIZ3ZfY4j3Sf7FFtDrYuLInQkIdCQT41mmyhpIntv0m24EhDKSD6oaAbjtKlHQItuGpgfGhTaeiswcOxEcWDq7KWy592hXOTVmg", "name": "The Nature Conservancy", "rating": "NA", "id": "90af6fb9fb926dde9f7103577cebc4150bbb1dec", "job_title": "Contemporary-Services-Corporation", "place_id": "ChIJq-m4EX3AQIYRJkn4Lhccp2E", "address": "1800 Augusta Dr #240, Houston, TX 77057, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.42318089999999, 29.7345943], "type": "Point"}, "properties": {"photos": [{"width": 750, "height": 437, "html_attributions": ["<a href=\"https://maps.google.com/maps/contrib/106788706324997826205/photos\">Erika</a>"], "photo_reference": "CoQBdwAAACkOCF20gLT9CCRzKcirzr8LrX4sdK04CIRHJKePLZNhT7cBwuMR6MM9HE5K2Qy7ajMiqlQXhL2gtWcwb1IQsrA6eMqMEgDgGqD7tNsJS3krrxT25371wYbNL_z3fW8Wbg17JcH5NkqWwepSjIyIaaXItYlWHuV4vLIS_aMfVBwJEhDAcJeZ7zRp78UMhncNfc8xGhSe8Foufbk9e3dEsGlr6gFwh47G-Q"}], "types": ["point_of_interest", "establishment"], "reference": "CmRRAAAASmxiw6dDYAXP6Sm8KXFm1JihRsnzwipRmUiP_BMHDgsOp-nw0Sr47O3s7Oop3UpeIseGzA3qctlaANeBMoapi5eQzATAqVfjLO8TugSX2OmRrQ_h0wr0IrizBGVg38-EEhASdwsLILfVTJK8RybdgNPaGhQ4dQSbtASMffOj-rseXaBuTvNWqA", "name": "Student Conservation Association", "rating": "NA", "id": "1c5ea7722fc0d99e9f7dfca55f5d9078224d51d3", "job_title": "Contemporary-Services-Corporation", "place_id": "ChIJQcqBXfDAQIYRErawO-goGj4", "address": "2990 Richmond Ave Suite #400, Houston, TX 77098, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-96.038102, 30.055621], "type": "Point"}, "properties": {"photos": [{"width": 984, "height": 985, "html_attributions": ["<a href=\"https://maps.google.com/maps/contrib/110279808588468038448/photos\">Peckerwood Garden Conservation Foundation</a>"], "photo_reference": "CoQBdwAAAP5YUSjHFj9A99jvkrZ5gxkd404fwhmS6UYShSiBOHmPj-FfhFmVNL9sBIDUYf0l-U_5lJau_uRNvNI5EdKZY7shEeXyiuxpJ6zwabgsIJEtNu3E2kVVPDmdNAbxr6EzKEX-78OX3bO0XRzRa1dYMjj4E518kiggVJYyhS4KBi0zEhA2jzb5PIGsCwHyqeUSqaY4GhSRo1YDb6jjdIVjqfA4zCWoFrHHEw"}], "types": ["park", "point_of_interest", "establishment"], "reference": "CmRRAAAAWn1G6vSLIxRJRE-S9ld6nYmhv_fsED1ZImeRbO_dfrSEgeA_6swNkmzAovDNuWubK4yB0eOJvizV0gF4bPfotdFT2VpODAjlaF8uEnoa6kNWGhLNS4fEyj7gWYoTuwn5EhBmRbqsn_LIqOxqBgYuQ6l6GhTzmtPinYp2ruSieyTSgk41-71wUQ", "name": "Peckerwood Garden Conservation Foundation", "rating": "NA", "id": "e618a4c618cd67ce4f5fdc165f640220ab3b53b2", "job_title": "Contemporary-Services-Corporation", "place_id": "ChIJmUR7pvHKRoYRIIl0o73bPGE", "address": "20559 Fm 359 Rd, Pine Island, TX 77445, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.64386449999999, 29.7515036], "type": "Point"}, "properties": {"photos": [], "types": ["point_of_interest", "establishment"], "reference": "CmRRAAAAjwL17nl7tdQxRgGlWqSgJLoXAN1AFjPvO8lIDDE18h-CPpqlmGXwK1QiiBCIX8VRDzdkKoAMFDCze7YL1A2jOFaBX-YZgWJnvVhalf4RoKY4i6V1RhA7JzTjYlSR0MShEhA5NS0gaikVp4vSm1rnnJUIGhTIaPcw-NpFGwXAh9UNcdG8OxWKtw", "name": "H2O Conservation Technology", "rating": "NA", "id": "30c07988ef8dfc62dac712b9d587daa4a36f2539", "job_title": "Contemporary-Services-Corporation", "place_id": "ChIJIWZRKeHKQIYRXxta3wOMGGc", "address": "1725 Hwy 6, Houston, TX 77077, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.5705632, 29.7714443], "type": "Point"}, "properties": {"photos": [{"width": 3024, "height": 4032, "html_attributions": ["<a href=\"https://maps.google.com/maps/contrib/108143329814504597326/photos\">State from Jake farm</a>"], "photo_reference": "CoQBdwAAADSrw5F0HilE8-6u4ZcR7aCblcyN52ZYQBBLomjdOMMaF_JXsHraZsyvndwWWr7znsOR9s30spJwhFCdbtMraM78p6ClSaK9hPOi1XuEInqVnVS43CHQBjawSpK5_Dj2Nhf4aGj2bh2MRBhmmiUihiDgJjf1t5YS6gT3jHJrFkAxEhBcSWQZ4GBkB7zIZkgTmLZqGhT8PjdkBJBVSZ44wJd0u8LbnxyYzg"}], "types": ["park", "point_of_interest", "establishment"], "reference": "CmRSAAAAPqMF8PLOkenmPkgWmvXysJ0A82unRmHmHU-j1J9Iv55N2UVWVso03euEw6CK7qcMz_USD_69NGh0yKCNC65iALC9Zqavl9VqVTV7GH6PZQevnnfYkgJ0_eZ-42yrt2ZvEhATovQfmv3RvHeFTxjO1T4_GhSVkAt39KoNnFo1ky8pQN9HAb15tQ", "name": "Houston Audubon Society", "rating": 5, "id": "050a5458d86bdd1cee7b09678bd6256d0a20a73e", "job_title": "Contemporary-Services-Corporation", "place_id": "ChIJlQOxwVDbQIYR2uX_TZl0TYc", "address": "440 Wilchester Blvd, Houston, TX 77079, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.56820189999999, 29.770778], "type": "Point"}, "properties": {"photos": [{"width": 1800, "height": 1200, "html_attributions": ["<a href=\"https://maps.google.com/maps/contrib/108765250995932379967/photos\">Audubon Docent Guild</a>"], "photo_reference": "CoQBdwAAAAVhJE4frjZpaNdJtpDBaT62CTbzPoEDeNiY8bJu-NhLYMI_s2uS3V7Axe5cHOr1no4I-cKtdvB6ns7odQNm2CDBHI6puPHA1A4q4pXWSgi3_US61J6_f1PObqwOFsz5NLVqw7EUtTxm1XEHhS4nHQ-Hn3-jwJHZPOtuXPgOUnz6EhDlBWuOtp7wPzDMQ_33mohjGhTKGsPBqgIuQqu_VzzHIFzPW3E_Rw"}], "types": ["park", "point_of_interest", "establishment"], "reference": "CmRSAAAAJ9eAjyRuBmLQPt34Leko2ZgGB_kTnLRn8a3Gf8knsf7DLxe1Un6Cu8i8sAOi6_UvN_7ZN4SirzIBBG7nWLAUxyKemzY2A0N243hFQi9tzGcR-cuyqubdo-rsshBfdEaBEhDFujoWKdmcW2MLLTrxcr8LGhSjfSObWPMg2p_XaSMz5TxsNisdJw", "name": "Audubon Docent Guild", "rating": 5, "id": "7ddd5daf76cc4979e2ba6b062322d1c77d5d1c07", "job_title": "Contemporary-Services-Corporation", "place_id": "ChIJI9XyNFHbQIYRtwHb8EtTpeU", "address": "440 Wilchester Blvd, Houston, TX 77079, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.44932349999999, 29.7803218], "type": "Point"}, "properties": {"photos": [], "types": ["point_of_interest", "establishment"], "reference": "CmRSAAAA5G7LohfbwRmV2S50KNxhrMO4-Rg5-HQjYaTlUwINFpJLWvsSvlRtUm8Yk4oQUETXtxolz56hjsayZmpxKpV-jcJTIEPYwtd9IXN5YveP2CCy_UNfk48GAyaRdxTPmeAcEhAsBLINRAmsDwT8MzbHT136GhR1nuUMfO9PPSB9ySeTbHVH62s-0Q", "name": "Coastal Conservation Association-Tx", "rating": 3, "id": "7258b034e119f31e82320bca6e72781ee9f79d75", "job_title": "Celanese", "place_id": "ChIJcekacM_GQIYRPzL13cgQrPk", "address": "6919 Portwest Dr #100, Houston, TX 77024, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.47039, 29.655454], "type": "Point"}, "properties": {"photos": [{"width": 5312, "height": 2988, "html_attributions": ["<a href=\"https://maps.google.com/maps/contrib/101184977609161362375/photos\">aug4</a>"], "photo_reference": "CoQBdwAAAMVs6rMeIukB5YuzYZahVU_VtFoQG2yl5mEg4gLWS89YGRf-yjenSBv77veVkkvsJupKEYGyuNtYSMQH0xIJ3dM3OUaZB3z8HNQuof00F0gtLVYeemFWUHmtiuWVQcfQ92Ea_Tv0TTbU5_Y3eZWvgZ87en0ivNAeY58SDrQOShLoEhCr_CkQl38WZV4ce3s-RVBLGhQFkL1BMz2JwzZZRvyYdp-AuXCnAA"}], "types": ["park", "point_of_interest", "establishment"], "reference": "CmRRAAAAVXH6_BI1vRaDMAY9AcfgyRi4z9_kdOHG-IQTy9vnZDiYD7HYvPt5fnCFZGnoHQrHDWancklWC2SflaJC4jEN0PhP6XM2Gay6POVR2LAHCLU9J7esvffm8oIwv84A7u6XEhDS5Yq-AWszu0XI12LIno5SGhTCeXc3kpEXo4_BDxx6YfoLCjbDyQ", "name": "Willow Waterhole Greenspace", "rating": 4.3, "id": "0127506e8071350c2d48f0ca56e939045297a0f4", "job_title": "Celanese", "place_id": "ChIJR6_2zTzqQIYRsA7wExgfDWs", "address": "S Willow Dr, Houston, TX 77035, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.4003322, 29.7388505], "type": "Point"}, "properties": {"photos": [{"width": 1136, "height": 640, "html_attributions": ["<a href=\"https://maps.google.com/maps/contrib/117056878997299689379/photos\">Marisol Brown</a>"], "photo_reference": "CoQBdwAAAFISuSMvtHR4uG-mPVQi4RbZmpAKxEHLpoA2OUBbv5T6G0SXFa7ykr9AG8xIJ_2CDw24IYz6IkAfnn51Ir-UClZQURWbj8DkIO-Rcp9nM8HPRjUpbDgNRhS5-upYauh87ZxyFbSMwDvSz3t9rBPB42neGINSXuqwHu7xb3t9_misEhC-JFEFo2L7ttqNDgOjy4owGhQg_-Cn5cMo9O0QsKO-1-OgnifvfA"}], "types": ["point_of_interest", "establishment"], "reference": "CmRRAAAAwpzfLNpLbCV_OIFoAPy7w0r7HVgC48UBL0bGeQMsqw9WGgFHCx0dB7YywlvQwTxeTW5aWz8tYeZQdOHJWR4EefOvOEbjdffImenXSdLvwIsl1qKUfr7x4HfirhMaqTQSEhCx9cPSP496bbNGpDtOT-hXGhRxg7HokbHuA8SyU0WYgkImVoiwoQ", "name": "Masters Fine Art Conservation", "rating": 5, "id": "a462c2eef4e22ea319485ae7b84f3d20756cbdd1", "job_title": "Celanese", "place_id": "ChIJp8u2bZvAQIYRbosnWz6cVmY", "address": "1612 W Alabama St, Houston, TX 77006, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.3876169, 29.794149], "type": "Point"}, "properties": {"photos": [], "types": ["art_gallery", "point_of_interest", "establishment"], "reference": "CmRRAAAA4zJ-p_8tL1Xir8iAU5kPv2GRbQ_U6WKGM--fU-pBFfZ0liKKAWngv1ze7HXbq2P5qPrbey3WmELGbDGJtRZD1f0wKtlUqBlo8IPWOLB3DYjrexV8i1h0FkhlNmvsOyiLEhD98kxr9YG8vgfCLDBhJUECGhRGREFTg5vfXKUIqwVwweJAikOE8g", "name": "Whitten & Proctor Fine Art Conservation", "rating": "NA", "id": "883a8c5ef35ab28e1630235ad65a6b16506a67fa", "job_title": "Celanese", "place_id": "ChIJ8YuXE6K4QIYRn1SF1hazFEw", "address": "1236 Studewood St, Houston, TX 77008, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.3858767, 29.7300997], "type": "Point"}, "properties": {"photos": [], "types": ["point_of_interest", "establishment"], "reference": "CmRSAAAAhD8A2b2GCVXgAKa4jd216Qro_wfjvNQciMkjcDYwrutNLTMAXurygI-scdqTIcPLgXCJDO_Af-f3GLNE2YjccNiw9-t8xf4TedUvKv2kDuTMEfJFiEXverS2Ws1Z-x-pEhAdi_TLKcljVPMgEhmB_57pGhRR3z5pDvvBSBCtqW4PRkV79uKJHQ", "name": "St Mark Fine Arts Conservation", "rating": 5, "id": "ea2d4bac6d74716b33f456dff3aae0cc0b43cca3", "job_title": "Celanese", "place_id": "ChIJKbDEoXm_QIYRcRFBlp0dE8A", "address": "4901 Main St, Houston, TX 77002, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.483218, 29.7482286], "type": "Point"}, "properties": {"photos": [], "types": ["point_of_interest", "establishment"], "reference": "CmRRAAAAOYJk5K1HPA3XveCXMjmBmK0Z3ddUWIwH10HtICuO6hW4TDF5O1XLx5ebshF_6YernnUdLCy4T2S9tduMp5J-fngZKHUMOO0Jh4vmLIOpy9ci_MaOVl27Z2rBroAuf0wNEhCEZfQZ8HgBBc8VHcX9z97pGhQiNg2dwvG400m4HV7PPwxWyMkfrw", "name": "The Nature Conservancy", "rating": "NA", "id": "90af6fb9fb926dde9f7103577cebc4150bbb1dec", "job_title": "Celanese", "place_id": "ChIJq-m4EX3AQIYRJkn4Lhccp2E", "address": "1800 Augusta Dr #240, Houston, TX 77057, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.42318089999999, 29.7345943], "type": "Point"}, "properties": {"photos": [{"width": 750, "height": 437, "html_attributions": ["<a href=\"https://maps.google.com/maps/contrib/106788706324997826205/photos\">Erika</a>"], "photo_reference": "CoQBdwAAAL0Kp9Jrrb8YvUtCs1JifvmGNz5qym1Ua0fK9iMV7jBvhamk9JFhj8MDG5RpDu45AmowlUf5qmiN1cYCwHgmuKU5VF8NWHtjJBrehRoWScLJObwXAric-_tZzHe-3penI8KasF50Kgmm9Xc-30FVuPYoUUumDUeDkXNFn2HiuU8vEhAtSHXjWkzJFmmzoSHlYiQeGhSn2-jLZMjFvuTJJDwL8Y_xKQfVGg"}], "types": ["point_of_interest", "establishment"], "reference": "CmRRAAAAVlNTPzaL_GdRSsnIT-m_MtKmhQauFdK6QJI9XQJDaVuvwexuzt4dGdoVgwktpk4yuzdLYFU1_Wr4z-GJ555o--Qvy0xIaHr7z6HBFTOA6yndFzd8EBEGuS_qnB8g64BWEhC-vV-tCI6GF1GYuJZkApv5GhTc8q2OCn5qmWFaXqwh7wtp1ktHbg", "name": "Student Conservation Association", "rating": "NA", "id": "1c5ea7722fc0d99e9f7dfca55f5d9078224d51d3", "job_title": "Celanese", "place_id": "ChIJQcqBXfDAQIYRErawO-goGj4", "address": "2990 Richmond Ave Suite #400, Houston, TX 77098, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-96.038102, 30.055621], "type": "Point"}, "properties": {"photos": [{"width": 984, "height": 985, "html_attributions": ["<a href=\"https://maps.google.com/maps/contrib/110279808588468038448/photos\">Peckerwood Garden Conservation Foundation</a>"], "photo_reference": "CoQBdwAAAEdir8g2wK_AWZVYbFlwfimxgelyY7LLlvxsisAMSFOrEOvluiaGtqmOa_VDDeCJ3v5hRUlTgJYqR5sie-HzoYM5gtIf7-ZMTh5y1EEPkUHx7pmgu0N_09iiCs56c1yEvCvoUhqmPhtLFg7edXcyOnr6zyeklwvgQVqCmCf1hbKgEhC3gRKAa4oQueHnbQ9A0BVNGhTKtZZF32imFC5hlBEDBRnfiZex3A"}], "types": ["park", "point_of_interest", "establishment"], "reference": "CmRRAAAA4jHLKnxqrMY2QsCElYOSsBymHS6yZudEx9b8ng_S2WYY4U1ANOvjXBi4suqAfEbfKYNZomopavRLgzBCluzwbDuAeeIMWPh2iDoXIl-jxJLyqwsDBXNKG3C_IZfy1160EhDbbHBpUjn5mw1pI3CSsSDoGhR3rMNazkLqUFt6l5RIeWTOPUJ-gg", "name": "Peckerwood Garden Conservation Foundation", "rating": "NA", "id": "e618a4c618cd67ce4f5fdc165f640220ab3b53b2", "job_title": "Celanese", "place_id": "ChIJmUR7pvHKRoYRIIl0o73bPGE", "address": "20559 Fm 359 Rd, Pine Island, TX 77445, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.64386449999999, 29.7515036], "type": "Point"}, "properties": {"photos": [], "types": ["point_of_interest", "establishment"], "reference": "CmRRAAAAK1sBUg7E_FnDueYsoLOikTzMmVK2f3NZR_ARy4I3qHFQanekGibA1MAZgLKbDMPhTrawOJWC-AT8thi3sCJpKiiwJuakelq0IsbQS3QXZayTOHRHsS4OUrt8bNUaVgr_EhDIcMxLI0ryo8rXpEfy4ticGhQpE2VoVQ5M25qOrDdF7cg5DWY93Q", "name": "H2O Conservation Technology", "rating": "NA", "id": "30c07988ef8dfc62dac712b9d587daa4a36f2539", "job_title": "Celanese", "place_id": "ChIJIWZRKeHKQIYRXxta3wOMGGc", "address": "1725 Hwy 6, Houston, TX 77077, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.5705632, 29.7714443], "type": "Point"}, "properties": {"photos": [{"width": 3024, "height": 4032, "html_attributions": ["<a href=\"https://maps.google.com/maps/contrib/108143329814504597326/photos\">State from Jake farm</a>"], "photo_reference": "CoQBdwAAALp3m6osi_uoTnPd8MypNCFBui5GbWzZAx3wnrNlad67lurrFDB0dSDt_QPsobWnzyP5K21TuNfN1w5w7rAghJ5DTbfao3qHuGbu9bl3viKraUAu9GyMSRB2mIWpe2TG-Jv44Wf1mOP0rP_KHZWK_1mccZYkCE9Q0co5H5CnIe2GEhD42rtI6ZV8OPB_YVOsWGzcGhSD192YGjBjaL9IVNP5eZpeqPIfjQ"}], "types": ["park", "point_of_interest", "establishment"], "reference": "CmRSAAAArYNBV1IGLplE9u7b7BF6xMf-YgqSi_6VWzhNDzOqPIODQGXV23tti_fi11gmb8tly47JLEBuz3hnmsSXVShok69vsaXgJwIPK_ZCUfLPUF-l05OdPyoOaoh1dVRH50sOEhAEBkU350iZA4wVWDB3InduGhTCKF1IkeP7k3f_a4LRq5V5Rj3IRA", "name": "Houston Audubon Society", "rating": 5, "id": "050a5458d86bdd1cee7b09678bd6256d0a20a73e", "job_title": "Celanese", "place_id": "ChIJlQOxwVDbQIYR2uX_TZl0TYc", "address": "440 Wilchester Blvd, Houston, TX 77079, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.56820189999999, 29.770778], "type": "Point"}, "properties": {"photos": [{"width": 1800, "height": 1200, "html_attributions": ["<a href=\"https://maps.google.com/maps/contrib/108765250995932379967/photos\">Audubon Docent Guild</a>"], "photo_reference": "CoQBdwAAAGdAeKtz6CPFfTIUoZJfMa3racDvem2wzeXwT32Fky34MmklnjFGRkbsEvDkP50kxXGzBy1g1YhJya8Z7KpjCulo7rSBB42nmg7uIqaUY2HB0BjxRJO62Bt-ZZJIz7ank81l2SyTDI0lTJhk11k3Pi7sVY64TKe4EymDJf-hmZS4EhBqhPXtOfD_1aCBf43AlYoYGhSEBYEAWymdNTLyLyws13xhxE6SQg"}], "types": ["park", "point_of_interest", "establishment"], "reference": "CmRSAAAAxvSe1Uj9a9Xqpe9L6EMmcBtzI7iqhRMRkXx_sUECsnFhQrWOsGbZuTRR62R6dO3ZObyRN0Ys5zeFLH_ThqkJdw23TcY15GLp295V7VZIyGddu4Li5QlunI80WyYqgkBSEhC0H2xbSPR2LWYtiO_I-6RkGhS_WEjQ76QKu5LZDmfbJSu6gPLylg", "name": "Audubon Docent Guild", "rating": 5, "id": "7ddd5daf76cc4979e2ba6b062322d1c77d5d1c07", "job_title": "Celanese", "place_id": "ChIJI9XyNFHbQIYRtwHb8EtTpeU", "address": "440 Wilchester Blvd, Houston, TX 77079, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.44932349999999, 29.7803218], "type": "Point"}, "properties": {"photos": [], "types": ["point_of_interest", "establishment"], "reference": "CmRSAAAA4nFp5_F9XLbdQdFXPlS-VfSee5WfARCoaOU0coYGfgAhxZY8gFFCaSToKuzBRL520646EeZqnB_k7PXVqsHETfB5YjvM9iRWdysrwTVwrDyeek5q3ctwtITV77WQlu4KEhDio26SztwlPTXEqjyVrcjhGhSwXhdDyqvslGR7mAQaFVFXmrbpMg", "name": "Coastal Conservation Association-Tx", "rating": 3, "id": "7258b034e119f31e82320bca6e72781ee9f79d75", "job_title": "Center-For-Toxicology-and-Environmental-Health,-Llc.", "place_id": "ChIJcekacM_GQIYRPzL13cgQrPk", "address": "6919 Portwest Dr #100, Houston, TX 77024, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.47039, 29.655454], "type": "Point"}, "properties": {"photos": [{"width": 5312, "height": 2988, "html_attributions": ["<a href=\"https://maps.google.com/maps/contrib/101184977609161362375/photos\">aug4</a>"], "photo_reference": "CoQBdwAAABWBbWpbtKCyMFTe-yhzUdwz-CRC-thbRalDEWdJQzUavcT0EG3LWPw_h9yrQ_sMx6eyJ9325JkLb-JXtrSJHHfP8cBO47PW8CajQ2MFKQgu7svF0Gez-bB3t9kS-BnxKxtpbN2SQJd-XS_sCMoKATjzWBaRY83XEU94qX7Yt1dQEhCip2NrN6GDNQOOs0bpyHfaGhS-ESGJjwy4OTNLNm74pF5tHO31pg"}], "types": ["park", "point_of_interest", "establishment"], "reference": "CmRRAAAA35N7VVWuYelqjPetkh96EdkxXywveisrUolqyUBpWviZZfuoCDGITaUp5xtw9i0cCOgLUrkwncjo13cY8KPxy94IqETDGfQpNb8gCXYWJdgg6guHsOvNUTjXCfU9Eqg3EhA6Gifzd8pXXR2F0-A4ma1GGhRsJL_UsFuN6Klq2oU_zsXEscLJJQ", "name": "Willow Waterhole Greenspace", "rating": 4.3, "id": "0127506e8071350c2d48f0ca56e939045297a0f4", "job_title": "Center-For-Toxicology-and-Environmental-Health,-Llc.", "place_id": "ChIJR6_2zTzqQIYRsA7wExgfDWs", "address": "S Willow Dr, Houston, TX 77035, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.4003322, 29.7388505], "type": "Point"}, "properties": {"photos": [{"width": 1136, "height": 640, "html_attributions": ["<a href=\"https://maps.google.com/maps/contrib/117056878997299689379/photos\">Marisol Brown</a>"], "photo_reference": "CoQBdwAAAJqxOb_jOy8AlFhUem3Bed02RsTPq-XH_beMvZ7AylM1eHXLhKQ0ckGbizPl7H3P9hD9xsR-7PUGm4i6kYdUXNKwpyP-mCqWZcsHlBYer-pTjh-Qs00tUVkQINhDdsdHGZM0t9kFE0LQ2ljEu_zL0t--MYybfU7_1RcJGcykgM2AEhBJcA_SZGYG3YB970T0uojGGhSeWQmEIVM1FmcnViuFEV5DMOdM3A"}], "types": ["point_of_interest", "establishment"], "reference": "CmRRAAAA85JTTokipwMxVS1_ILB7Iqw9VLJ2DTMkHmgq2IslR9moGY4R6GC6UWkB3bdC0qYU9HVwgYxBQI8CgvGwH5WvU6wVJ6e4qqaHKEPIqFtlUngjI-habFaX6KiB5X6PkJg-EhBF09x5STNhnig7PeC1dXbXGhQWhQbeuI2VXv4NYxGRlUoF9hnf1A", "name": "Masters Fine Art Conservation", "rating": 5, "id": "a462c2eef4e22ea319485ae7b84f3d20756cbdd1", "job_title": "Center-For-Toxicology-and-Environmental-Health,-Llc.", "place_id": "ChIJp8u2bZvAQIYRbosnWz6cVmY", "address": "1612 W Alabama St, Houston, TX 77006, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.3876169, 29.794149], "type": "Point"}, "properties": {"photos": [], "types": ["art_gallery", "point_of_interest", "establishment"], "reference": "CmRRAAAA2rgI0sQvrISK7dOwvoyGWX4fwdrfKNXslhop5FvAhAV1XwbHFimpe6kwCHVjQToD-y79AlmKsgWlD04mX7yey2xd4zEk77-gBSxzstOEleFkundgofmH3Dz1cO4xW9v2EhB98v2e5u5laINm04k56c5BGhQgF2d9DHTt3c_2e1Aj01-vIUhy-Q", "name": "Whitten & Proctor Fine Art Conservation", "rating": "NA", "id": "883a8c5ef35ab28e1630235ad65a6b16506a67fa", "job_title": "Center-For-Toxicology-and-Environmental-Health,-Llc.", "place_id": "ChIJ8YuXE6K4QIYRn1SF1hazFEw", "address": "1236 Studewood St, Houston, TX 77008, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.3858767, 29.7300997], "type": "Point"}, "properties": {"photos": [], "types": ["point_of_interest", "establishment"], "reference": "CmRSAAAADlHZxYzpQIM3PSMQyfCgk8K5BCBZ7uI2PtpqwUi4FjfA8XY-6DXTYuVT57mBAvaljBX454cWKF_JWnnjhSi332uClsNuo138zTj7LR6uLfenl5PcXcPeA-AgGlevTKqhEhCkF46BY-6cvkfmLjmBgHxNGhTXmFdr2VyQsrrlZQCihAQlvoV3uQ", "name": "St Mark Fine Arts Conservation", "rating": 5, "id": "ea2d4bac6d74716b33f456dff3aae0cc0b43cca3", "job_title": "Center-For-Toxicology-and-Environmental-Health,-Llc.", "place_id": "ChIJKbDEoXm_QIYRcRFBlp0dE8A", "address": "4901 Main St, Houston, TX 77002, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.483218, 29.7482286], "type": "Point"}, "properties": {"photos": [], "types": ["point_of_interest", "establishment"], "reference": "CmRRAAAAFs5UwJSDGC1XHH_dKe7k_lF6UfRdC_YyPQjHuRczsj1_4X0Hoxq-Wu3_qWln6YvQrOLXo3EEr2f7cWFXrOlQ1-GxQNPO6Amk1bDw-SCy8fsWw-bxanROuUCFFRq5Hg2jEhB4pdO8fpgeUmhj5Id5dOk5GhQBlVyLorBoR0bIL7rIOjveKO9dtg", "name": "The Nature Conservancy", "rating": "NA", "id": "90af6fb9fb926dde9f7103577cebc4150bbb1dec", "job_title": "Center-For-Toxicology-and-Environmental-Health,-Llc.", "place_id": "ChIJq-m4EX3AQIYRJkn4Lhccp2E", "address": "1800 Augusta Dr #240, Houston, TX 77057, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.42318089999999, 29.7345943], "type": "Point"}, "properties": {"photos": [{"width": 750, "height": 437, "html_attributions": ["<a href=\"https://maps.google.com/maps/contrib/106788706324997826205/photos\">Erika</a>"], "photo_reference": "CoQBdwAAANKfR7Mxallbnw3EzJ3UrZ7Has5p27NyRQqV5Zoj2VhB7Zcx2ln2p-2LO2qxQc8iJQnmwtFb_r0MDA6X5-twz4kJxO_WI-ptJ0PyZ-snYaBsRZmzYB_yLtHgRvmMB-RrxpdA-9XCbBgHgSWTCqEowTwFaqGxeEeGpIGjmvRr0ZrqEhDUmGbMlLrs4mXAlNLUTmnpGhQjkjBq2AqB-JRrbbU9cUUzG8TS5Q"}], "types": ["point_of_interest", "establishment"], "reference": "CmRRAAAATy9yAm_QziAWiGiTjyhqWjQ7GoIiXYQ2CmldXIYMviaU1kmKZ4S6poXgCb0sjRsyS8y6bASBVYZ_0xgcih4scVB6D3NS6bGwr6uz7S0zt6vA5ick2gqCZ6AgCBU9zdYXEhC28frcp9_0XlK8Z36Zj-TxGhT3oogVOx8nVJ8-6QfCvjPxPJuwCg", "name": "Student Conservation Association", "rating": "NA", "id": "1c5ea7722fc0d99e9f7dfca55f5d9078224d51d3", "job_title": "Center-For-Toxicology-and-Environmental-Health,-Llc.", "place_id": "ChIJQcqBXfDAQIYRErawO-goGj4", "address": "2990 Richmond Ave Suite #400, Houston, TX 77098, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-96.038102, 30.055621], "type": "Point"}, "properties": {"photos": [{"width": 984, "height": 985, "html_attributions": ["<a href=\"https://maps.google.com/maps/contrib/110279808588468038448/photos\">Peckerwood Garden Conservation Foundation</a>"], "photo_reference": "CoQBdwAAAFhCjn6cxesgpf6QAPTE0XVqQeE_RChW5xZK2SDJDBl3wjjEkQV9AmEM1Uh5wwyA2dTvhvnmRZBE_V-mJKeKH26q6w10eHgRNIufQAE2atwrHFnnLTNdNwh0AQvkoPtIWBSCS6K8Dam929u91UP9XxYn6D_Xdqp9UPnUg4_0tyj0EhCAyp3V5rKzevDQqGRD46rKGhQSBvQZjWYNcVKWBm4C-p6UumPQ1g"}], "types": ["park", "point_of_interest", "establishment"], "reference": "CmRRAAAAU7WRT00cUox41o48USSGxNjvWXOmo1s5QNyCFbTGF9tU_8egK2XkH2sn3S-CO6Yprcf2djAxQzBJLl44s-Xa4lz1aFSYk2J8CYZa3jDNSrmRBjHyopGbw-6qr_Kl3967EhD6nS5kWeFzzD5F1ryLMl_-GhRVgofZyiSenAgduoSb90MFyQYdzg", "name": "Peckerwood Garden Conservation Foundation", "rating": "NA", "id": "e618a4c618cd67ce4f5fdc165f640220ab3b53b2", "job_title": "Center-For-Toxicology-and-Environmental-Health,-Llc.", "place_id": "ChIJmUR7pvHKRoYRIIl0o73bPGE", "address": "20559 Fm 359 Rd, Pine Island, TX 77445, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.64386449999999, 29.7515036], "type": "Point"}, "properties": {"photos": [], "types": ["point_of_interest", "establishment"], "reference": "CmRRAAAAnNDoXOXmyhsjqCs9ni58X7XYOwNP6TMrokg_nGhy2i8Ni2uzYAIVSvBO0F_uqRD6QS17ikE3yDMn_OQfd4gP6w_UNui0Nx4ootnbDkC1elyj2WZjuGVDpd9zPg-QjaV3EhAVZ3ONjMTupcVfn52ORV8hGhTNRcHl7H9w2-LEfSsOWtPGZkMz7w", "name": "H2O Conservation Technology", "rating": "NA", "id": "30c07988ef8dfc62dac712b9d587daa4a36f2539", "job_title": "Center-For-Toxicology-and-Environmental-Health,-Llc.", "place_id": "ChIJIWZRKeHKQIYRXxta3wOMGGc", "address": "1725 Hwy 6, Houston, TX 77077, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.5705632, 29.7714443], "type": "Point"}, "properties": {"photos": [{"width": 3024, "height": 4032, "html_attributions": ["<a href=\"https://maps.google.com/maps/contrib/108143329814504597326/photos\">State from Jake farm</a>"], "photo_reference": "CoQBdwAAAJ5VdU_9VrdxJWJFkzwMzuTPQVa2jvgdbPCFHKxOxIbCQLkkwqdOECaBK8J7D2Egu1WP4D9X7LrnOYZcNVozroC0M2ddqruKMGGedmMyVyzatN9ZT8nyY_KbyDn9EJ4_aqSAVAasaAu-O2ruNd_aqNn36PxhxmCjvgeuhBwOmQo7EhB5q4kW0E0wlNOtgKZ2Vqe-GhSpUgOia7fhLUbLceO0qx7d8Ko8JA"}], "types": ["park", "point_of_interest", "establishment"], "reference": "CmRSAAAA_LnBJbvSMb-vZzXopZ-7Sx2gOfpZ7FxNgln3EX6pMwNGsLAkG17iHxbK-Y3AKFwrZX-fbPtXursqGT957GPHyQuocGCBpSSLQKq7QT2b3__Av2btErOmbEiPHKQK6haOEhDoYcrr9kcwfNmD3DnTOcQQGhQx-KHLFAc6SL_I6VwE5rb3qUcS0w", "name": "Houston Audubon Society", "rating": 5, "id": "050a5458d86bdd1cee7b09678bd6256d0a20a73e", "job_title": "Center-For-Toxicology-and-Environmental-Health,-Llc.", "place_id": "ChIJlQOxwVDbQIYR2uX_TZl0TYc", "address": "440 Wilchester Blvd, Houston, TX 77079, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.56820189999999, 29.770778], "type": "Point"}, "properties": {"photos": [{"width": 1800, "height": 1200, "html_attributions": ["<a href=\"https://maps.google.com/maps/contrib/108765250995932379967/photos\">Audubon Docent Guild</a>"], "photo_reference": "CoQBdwAAACJOrK1fuQ4FjR271gxIqKZKfRVrerx5dX0XXTjo4Ujdyx87Z_x8Yru_bMdz3QIXULjVPyWROxtW01AcXmYEnZqqyArYzXfNq54m7pbAugUR97JtSc09zfHjCjzeeCJ826gbVOfOay_gQ4IwaIjwr5_7aauLSSP-K8iATSRuQuf3EhBmfLfJkOGdL5RFRR6AZbG8GhQWGsvsZ5cbaj_qllMENoOYwfuRxw"}], "types": ["park", "point_of_interest", "establishment"], "reference": "CmRSAAAAZPs3rAogZR_xvpf5aQFzTAixS6jaAq6YiGRp66pI15mDxrWeiOjOK6sPzqBY5EReITo4B-6-dfYfIoPlC_kuotI2x9nbjY6ofxH9mp_JcgXKkF9Pt_I3rZz8QkLT9_POEhAwB8x9zBnOXPEYQOVfuSRlGhSHK_CMIElPZI3rO8dW84Ib8NIgSw", "name": "Audubon Docent Guild", "rating": 5, "id": "7ddd5daf76cc4979e2ba6b062322d1c77d5d1c07", "job_title": "Center-For-Toxicology-and-Environmental-Health,-Llc.", "place_id": "ChIJI9XyNFHbQIYRtwHb8EtTpeU", "address": "440 Wilchester Blvd, Houston, TX 77079, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.44932349999999, 29.7803218], "type": "Point"}, "properties": {"photos": [], "types": ["point_of_interest", "establishment"], "reference": "CmRSAAAAlhon6JnqzPxMioyoqUyi9vjmtGYucBAsHHt2VP6PjW1zM4l7sO5i3TRJ7J356w3IJwALakI9aQpfcPGqF7EPf35jNy2o3LOm4ZYovD_JlBitGoHdWsewknJcHD907qBREhDjl-Q6DKBKpw7jRvYwut_CGhQCcGhFPfWBrKwYxGPKqg8aeLtAwg", "name": "Coastal Conservation Association-Tx", "rating": 3, "id": "7258b034e119f31e82320bca6e72781ee9f79d75", "job_title": "Surveying-&-Mapping,-LLC-(sam)", "place_id": "ChIJcekacM_GQIYRPzL13cgQrPk", "address": "6919 Portwest Dr #100, Houston, TX 77024, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.47039, 29.655454], "type": "Point"}, "properties": {"photos": [{"width": 5312, "height": 2988, "html_attributions": ["<a href=\"https://maps.google.com/maps/contrib/101184977609161362375/photos\">aug4</a>"], "photo_reference": "CoQBdwAAAK8ZwQZGobb5qW6740-KIAXAWYDo6Ktbw56VcD8PKwZalFvDaLiyCR3str5zysdycRNIHys9ul4cxEdlg1IHd8e_yi-w_IBlN8601OIvJ1xf6rz4VryVZkXneeEQpAFGkcWM1A9UW1cvXC8dgARA9ZjUNXbnT7oGJO0dPlhJsfATEhDu-MX0n_0HLQDGcDR_PI-GGhQdSac3tXryox68QTLiPw46oSyCfw"}], "types": ["park", "point_of_interest", "establishment"], "reference": "CmRRAAAAy36epDsJwEtm7sEO10CWFVy4h59_whPXCk7jPGOkx_FqaPxTUiesDlTrt5GlDJwQQlUxXRN1H3fzFZsjJ8D5S1vDyZ6heV_WiyrpyVC9dnT4WdU0SYRqMxCD6YyhHSQNEhDfw7YdZxMH_XOOhS9XIJ1QGhRQO35P39HUMCER0WtyC4D4W0hihw", "name": "Willow Waterhole Greenspace", "rating": 4.3, "id": "0127506e8071350c2d48f0ca56e939045297a0f4", "job_title": "Surveying-&-Mapping,-LLC-(sam)", "place_id": "ChIJR6_2zTzqQIYRsA7wExgfDWs", "address": "S Willow Dr, Houston, TX 77035, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.4003322, 29.7388505], "type": "Point"}, "properties": {"photos": [{"width": 1136, "height": 640, "html_attributions": ["<a href=\"https://maps.google.com/maps/contrib/117056878997299689379/photos\">Marisol Brown</a>"], "photo_reference": "CoQBdwAAANdLUa1_XYaaRZpxqx87jhs54Nyr-nrNXU7EZIP_MssVbtEELLb5oL-e55H_EMb3JmjkbDKSFtVruZq0fD_gGVZ740fo36z0u_qCSedaYhXPz1jy7nX9EaQUCLE536RiUOTD7I4S2_fLns3Clf2Tq5KvaOpk40Y2uE6OQ1jY9qR1EhA0buUPGna6H3qcG4A6eHzXGhQhuW8rmn7Pi5uvGPxuXipmCjKZ3g"}], "types": ["point_of_interest", "establishment"], "reference": "CmRRAAAA2wew6mpYdRBlcqfAH4PIlk4P_LRtl9XBjRFDLDN7REj2no704jLcHwLmXTZ6g7RuHkw9Ihoyk6toCA0Pjhno6axbz9JDL4jxmkmZBJUzbbQkS846082X6mg-_Pd6BdjeEhDBGvKMNTd-FHwX33jkie7oGhR029Uve-3Xu8MWAByXO42xgZ6Yng", "name": "Masters Fine Art Conservation", "rating": 5, "id": "a462c2eef4e22ea319485ae7b84f3d20756cbdd1", "job_title": "Surveying-&-Mapping,-LLC-(sam)", "place_id": "ChIJp8u2bZvAQIYRbosnWz6cVmY", "address": "1612 W Alabama St, Houston, TX 77006, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.3876169, 29.794149], "type": "Point"}, "properties": {"photos": [], "types": ["art_gallery", "point_of_interest", "establishment"], "reference": "CmRRAAAAkodE-htLuzJzkybJXwzTec27_OrT6vUf0-QknqIFbAUCQt1czZxQRV-7WRrvu2fjSJJtA3j2Zpc2tV3msZEi9qHZpwcp2WI1pU4cZ-tJqHcY37UQ3kPWUtYDJsRDpTeLEhDNWY3wCrcFIBu3f5NdQ6YFGhT_vmRBAjOnu2FIb27l3oOoYuaKMg", "name": "Whitten & Proctor Fine Art Conservation", "rating": "NA", "id": "883a8c5ef35ab28e1630235ad65a6b16506a67fa", "job_title": "Surveying-&-Mapping,-LLC-(sam)", "place_id": "ChIJ8YuXE6K4QIYRn1SF1hazFEw", "address": "1236 Studewood St, Houston, TX 77008, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.3858767, 29.7300997], "type": "Point"}, "properties": {"photos": [], "types": ["point_of_interest", "establishment"], "reference": "CmRSAAAA_mY-3ooPNge3rjqQI4wW6gJZX1wScgLLHTZI94tdmilirj2yUufBuk7s-oY99MW79Emrl9fDLD_YWcWwDNrUDUNKAjQdVHJMmf8h5V_JNbq9JV31ORuAM6ZRimoJkj3REhChePCIUXbFuRoqiw434UA4GhREeXZhlx1k1LEZYrSUFOxv9mHcWQ", "name": "St Mark Fine Arts Conservation", "rating": 5, "id": "ea2d4bac6d74716b33f456dff3aae0cc0b43cca3", "job_title": "Surveying-&-Mapping,-LLC-(sam)", "place_id": "ChIJKbDEoXm_QIYRcRFBlp0dE8A", "address": "4901 Main St, Houston, TX 77002, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.483218, 29.7482286], "type": "Point"}, "properties": {"photos": [], "types": ["point_of_interest", "establishment"], "reference": "CmRRAAAAJ2H_D8LSwaNA2BFhY8LRph58hKldCLJJRA-yYucQeccafNebY6gnGRLZn1YKnGXjpwuRw18lzamkQsY-2gNRy8l4WhcjoRzQgHsbRroWDAcl1B3qcjGuS0QqWdSXFu2jEhBf0lQe6SaL5soh0P6snJ0XGhQAmPlbH0og2tgype24jEcKsEwssQ", "name": "The Nature Conservancy", "rating": "NA", "id": "90af6fb9fb926dde9f7103577cebc4150bbb1dec", "job_title": "Surveying-&-Mapping,-LLC-(sam)", "place_id": "ChIJq-m4EX3AQIYRJkn4Lhccp2E", "address": "1800 Augusta Dr #240, Houston, TX 77057, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.42318089999999, 29.7345943], "type": "Point"}, "properties": {"photos": [{"width": 750, "height": 437, "html_attributions": ["<a href=\"https://maps.google.com/maps/contrib/106788706324997826205/photos\">Erika</a>"], "photo_reference": "CoQBdwAAAK3YWiDCddSr6iXYS2DESB1yIzAQVmfvg4gD2oDS3r3M3J8_XMhg6oHjM4mRJdQGc4Jb1wBrZYKMC_W2Yb343Enqy_gt-Lqys9YS0XU-w9MM6NGiNqjzO4zthkmCqMZaBTtaBB9TOPSTEFc7FEBNZD_ku714bsMuiu79tSpJ_Zl5EhCrpqQpnVIw27l9j80nKcUpGhRyPaD3vV2XhQLhDeQQqs3hxTYTEg"}], "types": ["point_of_interest", "establishment"], "reference": "CmRRAAAAxqeH2PV3RLxYafbxHZrJGR89OlR-q9Pew3KvXbxbS3EApNmhQmn_ZTvFSfCekxcMgcHRvrhcboQ_2hntoX0zvpiT25ibHFrydtxKLEGcYx9YsjnQlrbJr_5UIt3sv939EhA-0qdwl2SI6Qp6xSs4USiRGhSWG88a6O-J1wUlvkMU7Vs_ilRbrQ", "name": "Student Conservation Association", "rating": "NA", "id": "1c5ea7722fc0d99e9f7dfca55f5d9078224d51d3", "job_title": "Surveying-&-Mapping,-LLC-(sam)", "place_id": "ChIJQcqBXfDAQIYRErawO-goGj4", "address": "2990 Richmond Ave Suite #400, Houston, TX 77098, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-96.038102, 30.055621], "type": "Point"}, "properties": {"photos": [{"width": 984, "height": 985, "html_attributions": ["<a href=\"https://maps.google.com/maps/contrib/110279808588468038448/photos\">Peckerwood Garden Conservation Foundation</a>"], "photo_reference": "CoQBdwAAAMehm8dx_2tcP8kuBUpDByBxQY6rC2ugIFT1IMbLCo3O2z-2zL2ttfNBfKSDlZs84L7tn9KhMgpXGaB3KXwhxCZK6tWcR18ZeCweGRVHSNA-soHQMtvkz5EFqP01EmAWXItNb7fgs_IApZRavq-8S3Yddao_OeRSFr9gHKTGuWgZEhDLax2Cp8405kuF8IIAq5k_GhS1ryC_sgSWUOv6rz4Cp6hCifT1Tg"}], "types": ["park", "point_of_interest", "establishment"], "reference": "CmRRAAAArNI1TrVX0CC7JIAni_ooNGZKSI7edNzjKRjKKiYs3xvV9RzoTpr7AOeCOkIBMGyaHmOQAQoCTp3T2gJH_kCN1w289qTc4aIOeGJ9RV6yDWDQLX3J44KZDYNUu1Vac2usEhCLMpKuPitpp8clOEsXF18yGhRvo-hQTUnccBXd7_8DO_Rfmj6Fdw", "name": "Peckerwood Garden Conservation Foundation", "rating": "NA", "id": "e618a4c618cd67ce4f5fdc165f640220ab3b53b2", "job_title": "Surveying-&-Mapping,-LLC-(sam)", "place_id": "ChIJmUR7pvHKRoYRIIl0o73bPGE", "address": "20559 Fm 359 Rd, Pine Island, TX 77445, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.64386449999999, 29.7515036], "type": "Point"}, "properties": {"photos": [], "types": ["point_of_interest", "establishment"], "reference": "CmRRAAAAbxJNQznqYO8NNIqm6Gr3mW-KXAIkZwqNsMER3nO9F8ycpeySthvZ_Grw3paDJ-6D8N5E7dd9UiGLNPN-JpP6ZL8aqb263VTtfIW3nHLdXiMIsDpCp5TnY75m-aH35SqPEhB7NpCT8-8C3HLDHYnMsODAGhRJ7OPhyM5mpEffJUUwP_sZ9cgnwQ", "name": "H2O Conservation Technology", "rating": "NA", "id": "30c07988ef8dfc62dac712b9d587daa4a36f2539", "job_title": "Surveying-&-Mapping,-LLC-(sam)", "place_id": "ChIJIWZRKeHKQIYRXxta3wOMGGc", "address": "1725 Hwy 6, Houston, TX 77077, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.5705632, 29.7714443], "type": "Point"}, "properties": {"photos": [{"width": 3024, "height": 4032, "html_attributions": ["<a href=\"https://maps.google.com/maps/contrib/108143329814504597326/photos\">State from Jake farm</a>"], "photo_reference": "CoQBdwAAAOsOSvqny_qyQNsm8kg8HR2pm9fq4_G7it9_G6TzDN58r7J_y8Gx4ucaHC2CPHUTIcnqca96Y0xDLUI-qsjUyiRnJZBaTDf3nLLLtCbniTMQNzzpcxaPM6mQ830Qg4VgDIvi_5Ie2TsMWOur4ZjqEsr7o2x19354wHRG0Gc0hppjEhAE9DwbIffypUPPbtJ0aY3VGhTCMKSeIwv9ihT1spnOZegVc4F13A"}], "types": ["park", "point_of_interest", "establishment"], "reference": "CmRSAAAAk3McLb0ROLEvkamBEY1ylYVVd1MwiZu5W2UB5V6HlLoM5WkDef0y2crKStLBAVTOrg1yOPBFNHY6GxW2HClvoXzrnqqNBNwFKKTA3f7yMtxuLIPaAlJu2D1EWQ3eIvW3EhAQ53Z1Pbbh2AkvNDPiPsWQGhQfLEezO2jt_pGFVgI434MlHZLW6A", "name": "Houston Audubon Society", "rating": 5, "id": "050a5458d86bdd1cee7b09678bd6256d0a20a73e", "job_title": "Surveying-&-Mapping,-LLC-(sam)", "place_id": "ChIJlQOxwVDbQIYR2uX_TZl0TYc", "address": "440 Wilchester Blvd, Houston, TX 77079, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.56820189999999, 29.770778], "type": "Point"}, "properties": {"photos": [{"width": 1800, "height": 1200, "html_attributions": ["<a href=\"https://maps.google.com/maps/contrib/108765250995932379967/photos\">Audubon Docent Guild</a>"], "photo_reference": "CoQBdwAAABxXbFHKKqLAcWJceW4WOgzi8DgkSsSbb-2aopk78Vyg-G1KsJHLPybW_iR2mLNuSd1SZIlKiO9lB4kmWzooSQbzXswQOBEFw0mznSHW4Q0EV8ZPJyyEoQMfx65yqcXUU_N7aZpRyg_Y7oOrYC1x_rn0qw8ELbomQMsycMO8i2DiEhDPEf9Iu1mJpwF5oQiSvdlpGhRny99MvqDaIv21-K4kuL3N9s8HWg"}], "types": ["park", "point_of_interest", "establishment"], "reference": "CmRSAAAAGnpW-gLCcVYR61l80KJscbUOsmqQEBjuAkhzEfxgMGJRf1i5HEl0tn2uXWecNWbWkU49uzcMVwMvj2tA1ngy7a-Qk1x5uPJUdLD_ik-I6G_Ym2XetXRKSw2LOUfkKR8gEhBxSnwxsFirCtWJ2UK3Q8HfGhRhOcEwVzdJKQKnxlwjsYs6_YLhcQ", "name": "Audubon Docent Guild", "rating": 5, "id": "7ddd5daf76cc4979e2ba6b062322d1c77d5d1c07", "job_title": "Surveying-&-Mapping,-LLC-(sam)", "place_id": "ChIJI9XyNFHbQIYRtwHb8EtTpeU", "address": "440 Wilchester Blvd, Houston, TX 77079, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.44932349999999, 29.7803218], "type": "Point"}, "properties": {"photos": [], "types": ["point_of_interest", "establishment"], "reference": "CmRSAAAA6mT8Rrov9SdiQcC5hnvwT3SUGXoMtQeBIkkLvrTrbJr-IPN-dtJ3QGY8xBBLRo380-4Jq3ZLC6nUnRoJyYI-_Ldo2tCeyFdc3Xc-JXAU9ODzPv3psXixTtpH8ySoEq1REhCTGAzVzKZ2Q5v80aJnfRerGhSUFmcjzSMuFNn_W8pHc9GVttBMwg", "name": "Coastal Conservation Association-Tx", "rating": 3, "id": "7258b034e119f31e82320bca6e72781ee9f79d75", "job_title": "Stericycle", "place_id": "ChIJcekacM_GQIYRPzL13cgQrPk", "address": "6919 Portwest Dr #100, Houston, TX 77024, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.47039, 29.655454], "type": "Point"}, "properties": {"photos": [{"width": 5312, "height": 2988, "html_attributions": ["<a href=\"https://maps.google.com/maps/contrib/101184977609161362375/photos\">aug4</a>"], "photo_reference": "CoQBdwAAAMLda6GriXpcecjxvWjSf0qqJgB-qepT8IMgefoWzcKdTtKGrN5XU--E2LKwhSlYQS0yqdSGscxCz9svKCoO4Tnn97Rkp54IXelYlxJDWt4vRY3JjGzKtElqVU60iT1Wlkk_OmerN_1gqwU3YZPoom-KeSTH6Du5v0D0cskBY4ZLEhC5vRyDKdeHW7X-q5EsgOWQGhQIfQbNlBupQZGSoH8Rh247EBwBgQ"}], "types": ["park", "point_of_interest", "establishment"], "reference": "CmRRAAAA6rXSPVfQglBQK3qSCeMN0QUCcj-wv6qovKe-139xips4ef1SHYPrUjTKQhYzTStpnBZuqyze0nlQEinaJ87ZmzGzQV1NtcoDWdMxMmS930YIrof2KSJjfAXoeeRM_a0fEhDfL29j79E_bMDHHVWnqNc7GhR_Iz_YEbvgFQymlLpm8CN1aVonJw", "name": "Willow Waterhole Greenspace", "rating": 4.3, "id": "0127506e8071350c2d48f0ca56e939045297a0f4", "job_title": "Stericycle", "place_id": "ChIJR6_2zTzqQIYRsA7wExgfDWs", "address": "S Willow Dr, Houston, TX 77035, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.4003322, 29.7388505], "type": "Point"}, "properties": {"photos": [{"width": 1136, "height": 640, "html_attributions": ["<a href=\"https://maps.google.com/maps/contrib/117056878997299689379/photos\">Marisol Brown</a>"], "photo_reference": "CoQBdwAAABWX9x4TaUchRZeZ1UaPv9PRkvrxfS6h7f4Zybhv2DA__2SNDhuee0wt-C7yGm9FYXMfgy6A8P2fa8smGa5JcAABuZCcyJ15EGSeTb3IaOzhiNtvjV9L42huK7RpDtv9cM28Hqp7im5s8MWPO1dUiXCwAS9fl6-LAojaq-OaZ9YhEhB2mCnnzeikkilrFaY6_72_GhS4R75tsvSLpa2m9Xououu4WtCmYg"}], "types": ["point_of_interest", "establishment"], "reference": "CmRRAAAAbJjdghp2DE1btxHqc8nZnLTfRsWKnBHGjtI_4g684LJUOvJPjLvB0lpge1oqT8l5Z92lUS3Uz1lfrUvYIjjzUs98fyhyLCK1EiNDVpgfngAp8nrhqdrvnDgWr3iy8A-mEhApH--Qo7rKOSIYsRYo0YrVGhTJgVePGWXw438tvds2RJH93J_PjQ", "name": "Masters Fine Art Conservation", "rating": 5, "id": "a462c2eef4e22ea319485ae7b84f3d20756cbdd1", "job_title": "Stericycle", "place_id": "ChIJp8u2bZvAQIYRbosnWz6cVmY", "address": "1612 W Alabama St, Houston, TX 77006, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.3876169, 29.794149], "type": "Point"}, "properties": {"photos": [], "types": ["art_gallery", "point_of_interest", "establishment"], "reference": "CmRRAAAAEWpAhKDZTzcEnI3ZHC1QsUIqR-tPH6LK2DuAicO7uSzx1DQEUFeXn0SPz4aAr01jorOHj4x98JAd7MxqKfhn7sWikfR4QpnyyqwTGe_RN_VoJ-R3dmKxnIqRPXwSO5nCEhAEPpGTOYcf5OnoXGRD_Sj2GhSiLsBiBa1JqhbydSjhXQfa3PlR4w", "name": "Whitten & Proctor Fine Art Conservation", "rating": "NA", "id": "883a8c5ef35ab28e1630235ad65a6b16506a67fa", "job_title": "Stericycle", "place_id": "ChIJ8YuXE6K4QIYRn1SF1hazFEw", "address": "1236 Studewood St, Houston, TX 77008, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.3858767, 29.7300997], "type": "Point"}, "properties": {"photos": [], "types": ["point_of_interest", "establishment"], "reference": "CmRSAAAAejRXIKDwQNyCyQ-vs5ieMYIRjeTh1R5b0L4tOCv5bQVfCuAOHGgDc0FAxPKpBQoG79gmXZXty27Fjv7yuuAA2XEX8UU5SP9Lbs2Ceyrg7wfNQkHvb8h6BgEiCCTYtJMzEhDgd7wO0EREXwbY6U3FAkZ_GhSe0kSviHE2WBO4fhax5Ca5tcuvaA", "name": "St Mark Fine Arts Conservation", "rating": 5, "id": "ea2d4bac6d74716b33f456dff3aae0cc0b43cca3", "job_title": "Stericycle", "place_id": "ChIJKbDEoXm_QIYRcRFBlp0dE8A", "address": "4901 Main St, Houston, TX 77002, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.483218, 29.7482286], "type": "Point"}, "properties": {"photos": [], "types": ["point_of_interest", "establishment"], "reference": "CmRRAAAA4WUXC887R8bkl051-mw0ZNunzM2DEHmnXyQ0UOFDv-TUBnsMBDRLkfwGo-Wjfyie8dkGVm6re9IQAzUAAXuKEjYSqTLJjWs4TiQffTAOeWrqgGU7UOKRmBmitfL2HAyXEhDF3PnitA_5XCBkQ8QB_oiVGhSyO2r0YI-4vtiu4UQGKzg-358sDQ", "name": "The Nature Conservancy", "rating": "NA", "id": "90af6fb9fb926dde9f7103577cebc4150bbb1dec", "job_title": "Stericycle", "place_id": "ChIJq-m4EX3AQIYRJkn4Lhccp2E", "address": "1800 Augusta Dr #240, Houston, TX 77057, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.42318089999999, 29.7345943], "type": "Point"}, "properties": {"photos": [{"width": 750, "height": 437, "html_attributions": ["<a href=\"https://maps.google.com/maps/contrib/106788706324997826205/photos\">Erika</a>"], "photo_reference": "CoQBdwAAAJEMum2LVtMDckTmKOEUWw73xRIZmNMymsi81wTLc5eeAxAvZ2PSEKdO81loAjqc63YcAkJMMl_Zl8QEITNyr1ptFtMPw1xj5HCg4cIkRMx3BL8X5Z7aTYq1XjnLKxKIC7YoPJ9VpfkL-3brcAHJE-Q8P_WIGgoXjSAjk_R5eZz4EhCJ6vxdaIlgKzoN4_73CK_fGhRs_qtWVQTe7QTLBiwnUtUIDIDciQ"}], "types": ["point_of_interest", "establishment"], "reference": "CmRRAAAAEtdUQlGOZErOKmENJdOOQv27qjDhojJgpRsXR7PGTcTWo52T1lViKtOz8GrRci4qZSKQJQ8dGzRwlD9Pa5T1ucswNA-QqApWaqJHazgQtCOuIGYha29xhdSR-_km11nsEhBxXVUihhEw8fAjkK_frDBfGhQqvi_LLtVq4OGYm8laAdrtS3foGg", "name": "Student Conservation Association", "rating": "NA", "id": "1c5ea7722fc0d99e9f7dfca55f5d9078224d51d3", "job_title": "Stericycle", "place_id": "ChIJQcqBXfDAQIYRErawO-goGj4", "address": "2990 Richmond Ave Suite #400, Houston, TX 77098, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-96.038102, 30.055621], "type": "Point"}, "properties": {"photos": [{"width": 984, "height": 985, "html_attributions": ["<a href=\"https://maps.google.com/maps/contrib/110279808588468038448/photos\">Peckerwood Garden Conservation Foundation</a>"], "photo_reference": "CoQBdwAAADLWQ9mpwHxgqh4W-KKE_WxZ394fpgedvvHcb9OUs3hTMbTH5PDOKDFVLbNUi-Obgs12N5NRzBmG--Ugw55ah4kzQUpCSAAc_LmdK1gDnDnUkHB9w3ZCnjOAPSNdvOcdhYu-Lu8VwsIlMzV6ZWxnGND4NJHWKvuH37urbpZ9hVQ7EhAQhqqkVJIrYiDM01aElIojGhSwAGXJK6MSbz6wOEGm8AGTDqD7lw"}], "types": ["park", "point_of_interest", "establishment"], "reference": "CmRRAAAAOD1l1GaShbiYY6Yz2w6yrdmWCBFXlV2d1dAhKz5hwVg-zls7NUOKLvTljO_g0f-AcCxYRkelAMWgW37EYkIZzerfOujc1g4g6JRY3QnA-XrA5g_XVl6gDKjM3xmueqEvEhB6K-0Eho_kGG4L2rcx8edFGhS8gBhuuZll117WCzUoRthiY-c2iQ", "name": "Peckerwood Garden Conservation Foundation", "rating": "NA", "id": "e618a4c618cd67ce4f5fdc165f640220ab3b53b2", "job_title": "Stericycle", "place_id": "ChIJmUR7pvHKRoYRIIl0o73bPGE", "address": "20559 Fm 359 Rd, Pine Island, TX 77445, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.64386449999999, 29.7515036], "type": "Point"}, "properties": {"photos": [], "types": ["point_of_interest", "establishment"], "reference": "CmRRAAAA1uqWpp7OQpvNhroPzemzdmMXGTgrcYR8h1qrN_8O0AhX2oDGFY57fc5566waC_sW5IRLvYW7suFfqWCmrR7e7JbYgMBafrkWh7XpA1MrJttGia2mjeOE6SnV1sUJJ84_EhBRoZoZKbavxfRU47HP0o2zGhQBzJtFGK0Py_ym8BImH8IlgLs74w", "name": "H2O Conservation Technology", "rating": "NA", "id": "30c07988ef8dfc62dac712b9d587daa4a36f2539", "job_title": "Stericycle", "place_id": "ChIJIWZRKeHKQIYRXxta3wOMGGc", "address": "1725 Hwy 6, Houston, TX 77077, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.5705632, 29.7714443], "type": "Point"}, "properties": {"photos": [{"width": 3024, "height": 4032, "html_attributions": ["<a href=\"https://maps.google.com/maps/contrib/108143329814504597326/photos\">State from Jake farm</a>"], "photo_reference": "CoQBdwAAAC2wdcBr5i9HRJN-uJAFckc_gdgHJrRxlbPlcfICN7yRZ7tOtQX9f_jcV-OjiFS_pIB4_o_BeXjjH_l5aFu4XmBF7Z7WUDqs7QpVlP7Mws1XH-gKnQ8ma0Ebsb7DPm8tmQQI9BNq2d-IoSwNdxos_hh_NVurNyM-vkMAUc-FrP0REhCALqLXbaVv7ihwURlIAWcBGhTyFzeYss5rD_lfLntV5vvA6tEvTQ"}], "types": ["park", "point_of_interest", "establishment"], "reference": "CmRSAAAAl9AE_3R3wJlzRYa-xHwsHVhtTbWJfuuMRVrs3krzBjQE6m4zVypPfsCFW8OJWLB-O0SdEMBxFQp594az9OME8ohu6EsBkAM-jQYcfOluxgvWaQaw-mTzJUiy4eSM1T6zEhAilSWJp4yXWvCxpNUuvbWZGhSJwiGHXvNGNpMktnv_X9E92TVIyg", "name": "Houston Audubon Society", "rating": 5, "id": "050a5458d86bdd1cee7b09678bd6256d0a20a73e", "job_title": "Stericycle", "place_id": "ChIJlQOxwVDbQIYR2uX_TZl0TYc", "address": "440 Wilchester Blvd, Houston, TX 77079, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.56820189999999, 29.770778], "type": "Point"}, "properties": {"photos": [{"width": 1800, "height": 1200, "html_attributions": ["<a href=\"https://maps.google.com/maps/contrib/108765250995932379967/photos\">Audubon Docent Guild</a>"], "photo_reference": "CoQBdwAAAERCXgnJ4t23bjMkLRcihtMK7D8FTBt6cp34RD39H-iCL25atBphwnVzxHg1iQ7L5AAtbyhyGGsB2LPnkOEmqdR-mxpTNvXH2BQ-B7QdAVjAW1QudD1dUX67d-NAT56elJGEwV8d6RmpT0npSaL50Y3qxC3NbEAPh2Zo_VV-pnteEhAqu2hWVKEIQAPw4Df1yZl2GhQzWRsmpBZycyy9mgeKsgQKaaQeYQ"}], "types": ["park", "point_of_interest", "establishment"], "reference": "CmRSAAAAHgSlYZAxvQPosqsTK6ddwLu0C_xaKuJiazd2nN75Ikhe9hLqHKRIxsxEf5Z8NOrr-uDvlzGBVedt377h9FppKvMA4ognSEJyVjIX28SYn8YkrMPW-xc7xBcRIcWSZLRLEhCZXstRHAp5fnPzToqo3zXlGhTxPbIl_VcohUZeKno8OJrdb1mFAQ", "name": "Audubon Docent Guild", "rating": 5, "id": "7ddd5daf76cc4979e2ba6b062322d1c77d5d1c07", "job_title": "Stericycle", "place_id": "ChIJI9XyNFHbQIYRtwHb8EtTpeU", "address": "440 Wilchester Blvd, Houston, TX 77079, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.44932349999999, 29.7803218], "type": "Point"}, "properties": {"photos": [], "types": ["point_of_interest", "establishment"], "reference": "CmRSAAAAmu4UFVQcDNcDQ43HR7WI_uBpUI9NsuHn6rssEJ_HJ_p3RZu8WJD6wCWhj_HjQvbt-lkXP_wZVQ_Fs4BgLbjvPLGGFxCoL3Kkyw-YnRGkuVcXtERDq6qKSnlgV6I5wjNIEhD68zCyNEywN7jC2LnECYZLGhQWwAEBp_WsWeWiM10pzybmMklJ6A", "name": "Coastal Conservation Association-Tx", "rating": 3, "id": "7258b034e119f31e82320bca6e72781ee9f79d75", "job_title": "Exxonmobil", "place_id": "ChIJcekacM_GQIYRPzL13cgQrPk", "address": "6919 Portwest Dr #100, Houston, TX 77024, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.47039, 29.655454], "type": "Point"}, "properties": {"photos": [{"width": 5312, "height": 2988, "html_attributions": ["<a href=\"https://maps.google.com/maps/contrib/101184977609161362375/photos\">aug4</a>"], "photo_reference": "CoQBdwAAAD-oeLB0L4SGnJDFP-YM694HLBUFjxF4OXzbWcLsgFe-W4TNBF7b9NXmV9BJ1JPhxtn08ld6_74QYjK9_wOAzE1RLYCgqm1gbndMJMqVy0mSvCkYoSyzGru4-ScS0OxNWsolu0wC4KJR1j0NsmcvN8pUvR3V6wmdapQwTi7mpalAEhBDuucmKUOk0WQcCQz0FnkuGhTDz6_lLailGpVGW3Zn5Oa0J6LC5Q"}], "types": ["park", "point_of_interest", "establishment"], "reference": "CmRRAAAAqYYilRbgMUb17y1wlU86PKkP1rGIYJ4EYCL0UwquQEExvqUxtyihQBYwkVJIzmDlGZC5c61UY8yVIBQjWV6S8qsapY6WBKKzEqFkBEFjKfpFCYH5ztHueulp2mNDpa6wEhBqPD5MTcOWXsDG5dY4-aUqGhT6sUf_mLByQDrBYtBWXdPJKWo6Gw", "name": "Willow Waterhole Greenspace", "rating": 4.3, "id": "0127506e8071350c2d48f0ca56e939045297a0f4", "job_title": "Exxonmobil", "place_id": "ChIJR6_2zTzqQIYRsA7wExgfDWs", "address": "S Willow Dr, Houston, TX 77035, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.4003322, 29.7388505], "type": "Point"}, "properties": {"photos": [{"width": 1136, "height": 640, "html_attributions": ["<a href=\"https://maps.google.com/maps/contrib/117056878997299689379/photos\">Marisol Brown</a>"], "photo_reference": "CoQBdwAAAImOiSx8HFHfbBXZlwJ3XSeB4VlWqQ_LVBhxcuRwI6hhhwVJKdYq2TLdrwPh9Pet6dZpegQeB5gCEv7ix1Juux3cNwy2B34cPGzaa5rDeJ7JL_yZpuMhM_ZCKvDAZcXiig7RqAloDZxf6TAqLEIKH1WU1iKGqsrwq-r7DpcZhA9lEhD2Nquw0VIUycBfc3_O9nW3GhSmWNAU0K3SJDkAID-GwcVrH9tCbw"}], "types": ["point_of_interest", "establishment"], "reference": "CmRRAAAAlJNGTq5o6o2RjMG3gmIby4cnBVRjcpNxhsotJXAl0QVSG5lxMRZ2Pk9kBH34SwjwPdh1ogjxNKlh4xtkoep6tlxlhJKH-yyC-K94Yb0tjelj6Jj7m6_kN15JnhdZs6yCEhDMT8pprtN-vAEWmoFkUmWVGhScgDdh-izlRGDhleXC32PGbMWS3w", "name": "Masters Fine Art Conservation", "rating": 5, "id": "a462c2eef4e22ea319485ae7b84f3d20756cbdd1", "job_title": "Exxonmobil", "place_id": "ChIJp8u2bZvAQIYRbosnWz6cVmY", "address": "1612 W Alabama St, Houston, TX 77006, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.3876169, 29.794149], "type": "Point"}, "properties": {"photos": [], "types": ["art_gallery", "point_of_interest", "establishment"], "reference": "CmRRAAAA8yu6syIvfmEgrItX5fOWg148-BF05G1ZNJ2sRlvl04g9LTk0z0Mctaa0QU1QtUR5J1BxMWprM7ksFoyVtgkYT6jZAM7od5yMNArdW5EE5UR1KFyOoobA2mNQ6dXcU5WhEhBRZ0ZhWZzrYqe7f3v4VOB5GhQ_1jhB5l6RKUFxA_d_CGoLmRclUg", "name": "Whitten & Proctor Fine Art Conservation", "rating": "NA", "id": "883a8c5ef35ab28e1630235ad65a6b16506a67fa", "job_title": "Exxonmobil", "place_id": "ChIJ8YuXE6K4QIYRn1SF1hazFEw", "address": "1236 Studewood St, Houston, TX 77008, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.3858767, 29.7300997], "type": "Point"}, "properties": {"photos": [], "types": ["point_of_interest", "establishment"], "reference": "CmRSAAAA32Dqnv4gk1CCPiO3_eUflNz5zfE1i7mR8BiRNhcoCKTHWLODExSOUuW9eTRFneakkglv78YlCBXCp3lDXxdLeu7T4wTAaPoZNi0QjMFqki2CwT1D49qDGCoOagAJIPklEhAYU0l0IPbrWZVMMuNiLG7iGhTgP_54F2I0pKpUT3ELkytK7pi1ew", "name": "St Mark Fine Arts Conservation", "rating": 5, "id": "ea2d4bac6d74716b33f456dff3aae0cc0b43cca3", "job_title": "Exxonmobil", "place_id": "ChIJKbDEoXm_QIYRcRFBlp0dE8A", "address": "4901 Main St, Houston, TX 77002, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.483218, 29.7482286], "type": "Point"}, "properties": {"photos": [], "types": ["point_of_interest", "establishment"], "reference": "CmRRAAAAFTLOB97gtaeRdV5YY6GaEsMQiffs44PhsaKoUOL3jU0SVVf2Ftky44ybvZ8vsk8JxBBNvM2iEKHPQs8ZGk0FYQnjDwsSFIdthdsVyhWXVYmWYIFe-1yt-6RjpIn37wa_EhBpkSunExwhEKOdyEMo8R98GhS65KR6ZkM7YJ0J6sPbChcB9Kaf7w", "name": "The Nature Conservancy", "rating": "NA", "id": "90af6fb9fb926dde9f7103577cebc4150bbb1dec", "job_title": "Exxonmobil", "place_id": "ChIJq-m4EX3AQIYRJkn4Lhccp2E", "address": "1800 Augusta Dr #240, Houston, TX 77057, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.42318089999999, 29.7345943], "type": "Point"}, "properties": {"photos": [{"width": 750, "height": 437, "html_attributions": ["<a href=\"https://maps.google.com/maps/contrib/106788706324997826205/photos\">Erika</a>"], "photo_reference": "CoQBdwAAAERrok2uCebu_8s3lw5Sn98KVYotul_COYdRxpzJUKrhQg7RleFpJ3zueFKi3ipIzC_NnLAD0A1TcorOFo4XajAd1apGrslzL90vWx72QBaGEOfZhr1CX64WX80aIROwy63COF11jsauJWUpEE1J95g7461OVhJD_iRA8mCtEpaNEhBsqkwmjVWgld_xPANGA1WMGhTKHe4Qlg47Ii0_jXo2uJMRBwPjow"}], "types": ["point_of_interest", "establishment"], "reference": "CmRRAAAAiNp7sSOmzhH0iQs9gQ5zuQnOOyG8z3ND5QtD_eISOjFdVv-ZD4iV3HdjhQ5wfLy9SodPNLhQpcCSqzypW5g5NXjEag1YHblsUo0OW2QzLpZ5KWE8-rYkl34XdyjTpr-rEhCR9hsYsKdimj3HrsYCfovMGhQWLkWgHoTfiedTFgnLs49AOBjFow", "name": "Student Conservation Association", "rating": "NA", "id": "1c5ea7722fc0d99e9f7dfca55f5d9078224d51d3", "job_title": "Exxonmobil", "place_id": "ChIJQcqBXfDAQIYRErawO-goGj4", "address": "2990 Richmond Ave Suite #400, Houston, TX 77098, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-96.038102, 30.055621], "type": "Point"}, "properties": {"photos": [{"width": 984, "height": 985, "html_attributions": ["<a href=\"https://maps.google.com/maps/contrib/110279808588468038448/photos\">Peckerwood Garden Conservation Foundation</a>"], "photo_reference": "CoQBdwAAALwXvRf8gB0o4C_JHsOVWVcAScPXMFU62ngD2bXDmcVYS3EaLeNeqbTwYA-i2-tqhrSw1gsqojCLAKjc2YlCzmbLLKjOUGgi1L1BftZ-uCpihVc-M-YSHrpq6FexcO-CN11Y8tSrbhxUxf_mpZkIEeXwUHfQHMe2AK79KYLrELpHEhDmNv2tRnlZJ2N_jlLJSR8MGhRXrEYDCXZwwqoO06vehvBcsFPZlQ"}], "types": ["park", "point_of_interest", "establishment"], "reference": "CmRRAAAA1dGBbBvzImuXgD5KPl9PmuTbiFPvg4eIbiQDA5E66SOF1mpGUC7C_32obNl7EuS94gikwkYrZDGo9Ck75fQ2EZS1QjUqwxTtSfylPA0RcFKyXUBXYQs3k61aGoSdLNzTEhBFdy-YHt3Il3f4ga7oh_N3GhSCJ52Pd4_mHPhfjgGtFylh1TKN2Q", "name": "Peckerwood Garden Conservation Foundation", "rating": "NA", "id": "e618a4c618cd67ce4f5fdc165f640220ab3b53b2", "job_title": "Exxonmobil", "place_id": "ChIJmUR7pvHKRoYRIIl0o73bPGE", "address": "20559 Fm 359 Rd, Pine Island, TX 77445, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.64386449999999, 29.7515036], "type": "Point"}, "properties": {"photos": [], "types": ["point_of_interest", "establishment"], "reference": "CmRRAAAAV_NKNNQT9rlVvZ0o5dRTfRC5i9XVaUT0sk6k7mgxBsnLt5Exf-9eO-NxdW5G2e8OKt0Bs5yCQWVzaOfuMe_MTH-MQHchTYaD4Vd8z9sKA_MVEiFPXPVpneILqOGzME-IEhCD5xjDN7m9PJ0yqmT2mR8iGhTTKRe7167TKp-sR1teku51FZeQNQ", "name": "H2O Conservation Technology", "rating": "NA", "id": "30c07988ef8dfc62dac712b9d587daa4a36f2539", "job_title": "Exxonmobil", "place_id": "ChIJIWZRKeHKQIYRXxta3wOMGGc", "address": "1725 Hwy 6, Houston, TX 77077, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.5705632, 29.7714443], "type": "Point"}, "properties": {"photos": [{"width": 3024, "height": 4032, "html_attributions": ["<a href=\"https://maps.google.com/maps/contrib/108143329814504597326/photos\">State from Jake farm</a>"], "photo_reference": "CoQBdwAAADDW5hzHkVQgepvAmdck60ha_DXYj7vMzmt6rSIEvvYHIESbAj4MeFlX0bkKXUw0W3uD1x_bNKg58ZRyHjpdp8wGhpehuH6zaL3X6D69rOJW8Z_1I2xy9TAyrTBsNcZLD48br022FF90MFbhAAYLpHuD5dbzx9lEqcxW94s-IAaoEhD2Ns0FGi63uzOp26HO1HN1GhR_eNNDbZ-7nehctljUBb0QwximoA"}], "types": ["park", "point_of_interest", "establishment"], "reference": "CmRSAAAAM6yOjnSh2byrfnLnLcXhO7udqojCiYYhR1GW_p3jERMr0VKUoCzyzT9ct19fjBAvJfvgse7UgiXD4RqVzMW19OkfwEXUpLxhI9VTVRsKJEYfKSSyYx6VqRL8IYTNFM-3EhCA_avCp83dRFLZzasHhAAFGhSv2rs-dVQz3f5CpO_VqSdWjzQwFg", "name": "Houston Audubon Society", "rating": 5, "id": "050a5458d86bdd1cee7b09678bd6256d0a20a73e", "job_title": "Exxonmobil", "place_id": "ChIJlQOxwVDbQIYR2uX_TZl0TYc", "address": "440 Wilchester Blvd, Houston, TX 77079, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.56820189999999, 29.770778], "type": "Point"}, "properties": {"photos": [{"width": 1800, "height": 1200, "html_attributions": ["<a href=\"https://maps.google.com/maps/contrib/108765250995932379967/photos\">Audubon Docent Guild</a>"], "photo_reference": "CoQBdwAAAGI95JgfltEv2625Q2Ldkri0cPFj9ki9jEfQT8XECDe32G85B5X0CsJiSlsIcLnrYvuOxn_NG5szGc9869MKBx-QTHj3lP4oHGvXNhCtqfDaCyRHcj1fSs4Nj1VK2PI9Qg_2FUzN9JSIbjpX_VRiZj1lApxG65zGp2SWBPTkw2yHEhCzC-NcZ26uedjF6KWR_mfYGhSLCg09ZhPzWHH1muW9KHD1qQoW9w"}], "types": ["park", "point_of_interest", "establishment"], "reference": "CmRSAAAATP3MWzoLr1wGbi-BP6gUIjU-uHDNgYDjyBl7gA57fpztRtlPo4hOxlsGHog_1zF7jGcojZzD7TGw7HVSO2roJlBm-rNaLbZS7SgcxZpd7RJA1936FzQZHrOC-wvaKc8SEhAy4PDQFSVFKAkLP5PET00IGhR0wAfmvNgwX3yw00mZNqNgOndQXA", "name": "Audubon Docent Guild", "rating": 5, "id": "7ddd5daf76cc4979e2ba6b062322d1c77d5d1c07", "job_title": "Exxonmobil", "place_id": "ChIJI9XyNFHbQIYRtwHb8EtTpeU", "address": "440 Wilchester Blvd, Houston, TX 77079, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.44932349999999, 29.7803218], "type": "Point"}, "properties": {"photos": [], "types": ["point_of_interest", "establishment"], "reference": "CmRSAAAAkDw5Xp-5FkRl-PVvyEzPCENb0W1Nbj3DFEA7khlr-vL7f-VJ0pxunh7QQpdTc5gsVyALLPZfArS4SbCO1eBDRZr0Ly-dFFtlFZg_D4P2fySJ3KhKluYus_9abxMbf-BDEhDvXENc8RavzqrPX6v628nQGhTCuzfAGZu4XpUNyyROyB-v7goxVg", "name": "Coastal Conservation Association-Tx", "rating": 3, "id": "7258b034e119f31e82320bca6e72781ee9f79d75", "job_title": "Stolt--nielsen-Limited", "place_id": "ChIJcekacM_GQIYRPzL13cgQrPk", "address": "6919 Portwest Dr #100, Houston, TX 77024, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.47039, 29.655454], "type": "Point"}, "properties": {"photos": [{"width": 5312, "height": 2988, "html_attributions": ["<a href=\"https://maps.google.com/maps/contrib/101184977609161362375/photos\">aug4</a>"], "photo_reference": "CoQBdwAAACA9P5GRf8yiNyzfxeCUgUoKeS38fBktFrfFTYwzxqyCssokbDJJ87PeTr5tBXC0Y_qftjptktQb6CawPgd1ExQgJ1CH-frkNxS5In5aKdEl5o_nUmVuwhm4b8Dl5Mtrzx8lbrKgj-JtgFdDNJesNBYNtT4FiowFF2zZOc48jLyiEhD0NfvDFsI5bCESoSUW7m9AGhQn1RWvW_v3ogTqZ5z9nwqIIrLajA"}], "types": ["park", "point_of_interest", "establishment"], "reference": "CmRRAAAAPRchBLl9pMtVAauYPAeynu8tYsi6rXuvMK3IgSxi_uVb3kEEAuVHAPUb0fJ0XAhreZga8MxL879zOO2vrJqxPUmLGwGwkayYu-DFcK4Y7V7jnp-qqqUvgYdQ2bkR4jzdEhC4ixV9hfVrhcN2Csm86rOeGhRDlDJneAz4NRAYE6dyt8PIh_UYZg", "name": "Willow Waterhole Greenspace", "rating": 4.3, "id": "0127506e8071350c2d48f0ca56e939045297a0f4", "job_title": "Stolt--nielsen-Limited", "place_id": "ChIJR6_2zTzqQIYRsA7wExgfDWs", "address": "S Willow Dr, Houston, TX 77035, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.4003322, 29.7388505], "type": "Point"}, "properties": {"photos": [{"width": 1136, "height": 640, "html_attributions": ["<a href=\"https://maps.google.com/maps/contrib/117056878997299689379/photos\">Marisol Brown</a>"], "photo_reference": "CoQBdwAAALAQFvglyx3yKKAQ5tcVFgDHvN6sLGXqp6CVCKasLIXYssixjRgIYotW8gsNfQlaB_VJduS_GWtmt9cIoXuKhrrScg8IvTbm2BlSO-mauRqgcZCGmvvuR8HIGLSTsinvLu2bX5Y2Aq7gJO1KiX51XH1cDt3ExfjeyStM_TZa_popEhDJ0puHwSsBrki9__KLehXEGhQDQN_b3fsKY1F6UMFzU6h6ycgJaQ"}], "types": ["point_of_interest", "establishment"], "reference": "CmRRAAAAAaTRH43QTicUQt5UVgrKtbqtgWTQmXLxO1BgwilXaScQN-RB0wJvYfBC4xd8A3JBGtz41utf6iRtcyaYou60hrcj2CEh_eDR3jOLT0zgsBwIQtTMjGu-psHjqjVqAw9qEhBI3P6hUD8Ipj9lSLjsy3IlGhR3u6tTPIRlKNYDbNHRnL3ivGTDQw", "name": "Masters Fine Art Conservation", "rating": 5, "id": "a462c2eef4e22ea319485ae7b84f3d20756cbdd1", "job_title": "Stolt--nielsen-Limited", "place_id": "ChIJp8u2bZvAQIYRbosnWz6cVmY", "address": "1612 W Alabama St, Houston, TX 77006, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.3876169, 29.794149], "type": "Point"}, "properties": {"photos": [], "types": ["art_gallery", "point_of_interest", "establishment"], "reference": "CmRRAAAAyprMoo9iLB2XVkyUxJRcij3_3PfdUKxQfKfVwtpPNZtL3jeFzLdhE9mLg0f-CyME6B02wZHkwA7RtWLm5WQN2YN9eQkOeYpapDcX4M8gQDynSDCO4NhSCxKm3xrF8c3QEhDjc3h31lfZaSt2xLwH9r52GhRbv9d6wBdMUrBN2pgbjB3ubocEQw", "name": "Whitten & Proctor Fine Art Conservation", "rating": "NA", "id": "883a8c5ef35ab28e1630235ad65a6b16506a67fa", "job_title": "Stolt--nielsen-Limited", "place_id": "ChIJ8YuXE6K4QIYRn1SF1hazFEw", "address": "1236 Studewood St, Houston, TX 77008, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.3858767, 29.7300997], "type": "Point"}, "properties": {"photos": [], "types": ["point_of_interest", "establishment"], "reference": "CmRSAAAAF3TSS3cVuiV18TSILVsIw2Fuzm48dEQA7JvDAuym0CN2olV-Ej0bB1vcA4IGmhEHGTqL1dKbNTcLIUGsoS4hMTsDdoowbyBRx6Jk1RIv5w0jlfPtgpkPZ5-O1Mvr0OCoEhD7rrKAqcDdueD-DlI8QiqMGhTdQnNXVkv1KTQ5RGSkkJ7Gt99a7A", "name": "St Mark Fine Arts Conservation", "rating": 5, "id": "ea2d4bac6d74716b33f456dff3aae0cc0b43cca3", "job_title": "Stolt--nielsen-Limited", "place_id": "ChIJKbDEoXm_QIYRcRFBlp0dE8A", "address": "4901 Main St, Houston, TX 77002, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.483218, 29.7482286], "type": "Point"}, "properties": {"photos": [], "types": ["point_of_interest", "establishment"], "reference": "CmRRAAAAxekaslYwMdeUblLkFO8Wzaw2teZ75UuRe_rcmB5MuYveU6Zmz60v1MAMRB1TXioGYpF0sNZYGQ5IJwKw3mjzvgqf-qAgheOYrN1YvNs-sZSeOC-1cHrPHrE6cgmW7M3aEhDGB88KPoQDY6Vo37WuHZojGhTFzTrr-iJN9aXBgL3NPzTScgRGpA", "name": "The Nature Conservancy", "rating": "NA", "id": "90af6fb9fb926dde9f7103577cebc4150bbb1dec", "job_title": "Stolt--nielsen-Limited", "place_id": "ChIJq-m4EX3AQIYRJkn4Lhccp2E", "address": "1800 Augusta Dr #240, Houston, TX 77057, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.42318089999999, 29.7345943], "type": "Point"}, "properties": {"photos": [{"width": 750, "height": 437, "html_attributions": ["<a href=\"https://maps.google.com/maps/contrib/106788706324997826205/photos\">Erika</a>"], "photo_reference": "CoQBdwAAAOLKTtf0LAPMXlZ1hOkoIfo06rwoNerVdwL1TxuXsYSWxJG9ilEwcql7zKCC5NRr9fP3veIbDrWEjr_Eya3y-BWf73rg7KmM9VyWIlBVEcNalDagwBgSuFlaXknguPXmWvTOzNJCtWZWapulhBSAYJ6Xp3w7lsznl4xXPmG3JqmkEhDritefRkPUV-nlkFXrdJYRGhS36SlOtYaVd2PnRtuMsJXQhIvf-w"}], "types": ["point_of_interest", "establishment"], "reference": "CmRRAAAAA4Nqs1oGdf8pq7Q7OxmDWL9rSh5WdUJsBsO_aYMfJY4nokfTn6SGMBaWxMppAvMUaW_xqtUi5AVzkWXy8oK0t3g9hKLp2s_toNoCnMJ6UH4hqrrlQ5-7v6qhEAdv3JIEEhCLiiSbJP1Mr9xlK3NYouJlGhSnBHp0_6ic2VgvnUkL40oblqbwrA", "name": "Student Conservation Association", "rating": "NA", "id": "1c5ea7722fc0d99e9f7dfca55f5d9078224d51d3", "job_title": "Stolt--nielsen-Limited", "place_id": "ChIJQcqBXfDAQIYRErawO-goGj4", "address": "2990 Richmond Ave Suite #400, Houston, TX 77098, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-96.038102, 30.055621], "type": "Point"}, "properties": {"photos": [{"width": 984, "height": 985, "html_attributions": ["<a href=\"https://maps.google.com/maps/contrib/110279808588468038448/photos\">Peckerwood Garden Conservation Foundation</a>"], "photo_reference": "CoQBdwAAAGVznqfVRbd9xRLgpfuzGB6n__CDaEW1d9vDttaVzZsHg4dG6mFmEXfxt-krxiqUlSiDvPRHkad_t_bD8riKbX2RQeCDp2Y4VuRToOElNamesUhXDkacuopxvSH8sr1on-3vaxLAjoc3GjVJsN3Kt7ai1pFrSMemYaxqJkmpPhG1EhBfE8xd_algKU6CDO4AZV_LGhSlPFqVMvcd5kec-FGXDHnQJQjWeg"}], "types": ["park", "point_of_interest", "establishment"], "reference": "CmRRAAAALzRn6BCSWQgCJRXuwFfsiJ2TJY6cXkFI7f551JCQJUod80IP1OIpWeYVzCWy_5tXZ0ZDjsYjRSr7Lc_Djj_1_8pzBOYtcfKm3NHZXmI8bvajGyo2n5FGxmo84EePmvIoEhCGlCwWkCtR360J3xk3Xg8xGhS7Pa2MCdcKdEv_IuOF3RkipcfR-A", "name": "Peckerwood Garden Conservation Foundation", "rating": "NA", "id": "e618a4c618cd67ce4f5fdc165f640220ab3b53b2", "job_title": "Stolt--nielsen-Limited", "place_id": "ChIJmUR7pvHKRoYRIIl0o73bPGE", "address": "20559 Fm 359 Rd, Pine Island, TX 77445, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.64386449999999, 29.7515036], "type": "Point"}, "properties": {"photos": [], "types": ["point_of_interest", "establishment"], "reference": "CmRRAAAA9OHPAXMc3YdIYdHNizdoKrdeUWewawCKOPKOhzggy1R2O-BVVzJw8brngIocn55f3uBSUA-4_Xv9ZoRIxrllRCWCM6wetkwBUuHHJlFaqLsqLBY5i3ebHAb1NWTZBN7bEhD2kOB1kA7AqROcKvEp8q0hGhR2G1GkJg9mocWZs0I9u4Cz3PV_Qw", "name": "H2O Conservation Technology", "rating": "NA", "id": "30c07988ef8dfc62dac712b9d587daa4a36f2539", "job_title": "Stolt--nielsen-Limited", "place_id": "ChIJIWZRKeHKQIYRXxta3wOMGGc", "address": "1725 Hwy 6, Houston, TX 77077, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.5705632, 29.7714443], "type": "Point"}, "properties": {"photos": [{"width": 3024, "height": 4032, "html_attributions": ["<a href=\"https://maps.google.com/maps/contrib/108143329814504597326/photos\">State from Jake farm</a>"], "photo_reference": "CoQBdwAAADD7lmS6iluzmCnYhLl_Qj2vxQ6JM9E7jWT_n1cxHm8ge3MskIMSr9vKqeNms6tyutRNjdp-DSbIoNHZGKraHe3Ko2nw1JwAY1jTeo6v-ugZyTuB5dn67S2rPWqoQzNjgYzV3S5Nc6faplmTh0gBnyRLrwOWbSgyzjTRlJ2mSCdAEhDaz9WWNf16XhdsHofUySpkGhQnUgGW-4LDHbxTGkMWN9yc8NiHrw"}], "types": ["park", "point_of_interest", "establishment"], "reference": "CmRSAAAAsTdPHgKxmmbkSX14NVJm2fM5EalLTOtiajoMPJyKhS40DRMS7W6LgHox2EzEBVzSa9MUpFK9lEunjGARBxIj-lATmWkyY9QFcTXcZ2mbb1DS47j5wuzgvhPfcdA3W2AeEhBJfoxZWbLeqxj8VLM-730tGhRRAguDDF-wwhKdDdhtWhefUwzPAg", "name": "Houston Audubon Society", "rating": 5, "id": "050a5458d86bdd1cee7b09678bd6256d0a20a73e", "job_title": "Stolt--nielsen-Limited", "place_id": "ChIJlQOxwVDbQIYR2uX_TZl0TYc", "address": "440 Wilchester Blvd, Houston, TX 77079, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.56820189999999, 29.770778], "type": "Point"}, "properties": {"photos": [{"width": 1800, "height": 1200, "html_attributions": ["<a href=\"https://maps.google.com/maps/contrib/108765250995932379967/photos\">Audubon Docent Guild</a>"], "photo_reference": "CoQBdwAAAFywpdp8bVWxigDxV_p3d56UkjiEdE-vVUzkRFLGduOOvifH_rDTwo3UkLwgxEv3T7lLe3FEnVS5gq7Lwtl8xcJPWxUP87c_RuPn1NRhhvhTvZ2e-XKtyqvhLMNLdnfmVjX4E4AlNuPVpRHV1LfX0ej_R--xUJd3YMNPwoh4LdQOEhBWezaaySSSPZhz01CJoBk4GhQKtSKStAI-Jk81hu0YMI0yRXgU-A"}], "types": ["park", "point_of_interest", "establishment"], "reference": "CmRSAAAABxAp_vXXik6DmLM6LCSfp0x5QcHxzAhMLtEzBA3JY7AbuS72jke4OY0pEZNW1UbdNewDFdfoOKY_nlekRWhw-F7QobBn6hjZ9-4sNoYa_vc7zI6DL5OvORTOkAVFef4PEhCaHAYY9scj7-pSgG6e-QwjGhR5bWut2UMsKovWBtPS3cxL6PKqaQ", "name": "Audubon Docent Guild", "rating": 5, "id": "7ddd5daf76cc4979e2ba6b062322d1c77d5d1c07", "job_title": "Stolt--nielsen-Limited", "place_id": "ChIJI9XyNFHbQIYRtwHb8EtTpeU", "address": "440 Wilchester Blvd, Houston, TX 77079, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.44932349999999, 29.7803218], "type": "Point"}, "properties": {"photos": [], "types": ["point_of_interest", "establishment"], "reference": "CmRSAAAAPBHsIMVImHUMWORVc-FFmMe7vAf2I3vjVcpB3vXvyVEO33tel89JLktkAoOy1XRt9h6KO4A4JOItGowr91gyCGzQ6xuP5Poi_aITLk2cLNzMPJyxQvmPM9IvRtI5Sj8FEhCax93yY9ZvlvxnAuXqYjcbGhRdhM1Y4AEF363WFFwcrXklPUm2Ow", "name": "Coastal Conservation Association-Tx", "rating": 3, "id": "7258b034e119f31e82320bca6e72781ee9f79d75", "job_title": "The-Hertz-Corporation", "place_id": "ChIJcekacM_GQIYRPzL13cgQrPk", "address": "6919 Portwest Dr #100, Houston, TX 77024, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.47039, 29.655454], "type": "Point"}, "properties": {"photos": [{"width": 5312, "height": 2988, "html_attributions": ["<a href=\"https://maps.google.com/maps/contrib/101184977609161362375/photos\">aug4</a>"], "photo_reference": "CoQBdwAAAOsCYtSUYnWMSuIqP2BZzztx-kE3Du1OJYSMzWCkzXnBNskeC4H--RXRImP587crOZhW2-g6RbUl6Qtnb4AokQ5iugmGi-3WWHYqb2KM1N8yMSkstrBnR77vGaz-kAwlfkWtCny6jy9KOV4JHDLcA7Bxnq67rIB_q1GiA6mV-ghBEhD4MrdwUk0HksmBy08IHI2eGhTZ0uaaZOYmOeeZkwvlpXsj0MxomA"}], "types": ["park", "point_of_interest", "establishment"], "reference": "CmRRAAAA5QM0XaUJ-XWsAcTNhk-2t0N6zdutwCs3oe2brbBk9qcB23Rz02eJFcBq550Mm_Q46uF62CFDZyzzajNxG3rL7QbB8aTjdNLXUZTwUH-V6Ik2FHryxg5cYzag4FIYcJacEhBs07R6NMam8D3O6QrjiTnRGhRVA2D0FabXYov7eBY9K6RlrDl_ag", "name": "Willow Waterhole Greenspace", "rating": 4.3, "id": "0127506e8071350c2d48f0ca56e939045297a0f4", "job_title": "The-Hertz-Corporation", "place_id": "ChIJR6_2zTzqQIYRsA7wExgfDWs", "address": "S Willow Dr, Houston, TX 77035, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.4003322, 29.7388505], "type": "Point"}, "properties": {"photos": [{"width": 1136, "height": 640, "html_attributions": ["<a href=\"https://maps.google.com/maps/contrib/117056878997299689379/photos\">Marisol Brown</a>"], "photo_reference": "CoQBdwAAAIkO4iisqUFopiP3CAF75bej-SzHmWNPNnoJWE3SbX1D3OMmDTLueWhYuFVgnCmi8F_jGaaTByDP6d9KuatBxV-gnKybB37WBPxM6kwXjKenvqrI3K4XSeui2yf1osDibL9rjKtGQ7dL-cZMFflWseVkQSdTRFYbKiXXvVYHrUEgEhDQPpGv00siq5Av6UoliQXUGhTHE-ADEXz8n2Oi46u8Yr5H9MF9mQ"}], "types": ["point_of_interest", "establishment"], "reference": "CmRRAAAAw-plzS5gMFDwInHzU8aYbOJEfzVm4lF-s9ySMcbxG0OX93HcbL6aEjdCKhChJBsCDF_sP6mLKIgWRzYI8mFsIPcJLp5n734NJUbC641-vtg-sZkk3AqW6jcfFuMFoCtkEhDbTxBo8QkfiHYE_Qb2aNb2GhTiWk0YaF_2rd9MJo2ZrsKeZOYRag", "name": "Masters Fine Art Conservation", "rating": 5, "id": "a462c2eef4e22ea319485ae7b84f3d20756cbdd1", "job_title": "The-Hertz-Corporation", "place_id": "ChIJp8u2bZvAQIYRbosnWz6cVmY", "address": "1612 W Alabama St, Houston, TX 77006, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.3876169, 29.794149], "type": "Point"}, "properties": {"photos": [], "types": ["art_gallery", "point_of_interest", "establishment"], "reference": "CmRRAAAADq1Tc8QU-V9Cy_ooF1ZmONCcETI1jJ-jHMTVwJefUt4qht7dzOdO2Ij3h0i_z1RGh2CtPNAzyciPH7ANdFJaiDkgRqt5z6CinbGsnbr50CdFPONvT1fxdqHLe1erxtPVEhA3__3pPMv6lGRCjeS0smyVGhSSCxqT_6lTIshjgKAfO_LbTkrztw", "name": "Whitten & Proctor Fine Art Conservation", "rating": "NA", "id": "883a8c5ef35ab28e1630235ad65a6b16506a67fa", "job_title": "The-Hertz-Corporation", "place_id": "ChIJ8YuXE6K4QIYRn1SF1hazFEw", "address": "1236 Studewood St, Houston, TX 77008, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.3858767, 29.7300997], "type": "Point"}, "properties": {"photos": [], "types": ["point_of_interest", "establishment"], "reference": "CmRSAAAAvjpWQt-gyo_VCoLc9tzHOCGZmOdqmPyWbm9-n1foNSzvjjtA9yOf-Ojj32woVPJ-QOBu4dYDZopu5GXV2pHZYIa2sD3M2Vm0egBXEIjcvnvPdXo9c0ty5zvRtE2TKgXtEhDzTcQ3IZCHG_XxPBRUpzHsGhQIU0ZHTYaTQj1fJRQLWm86FHU1ug", "name": "St Mark Fine Arts Conservation", "rating": 5, "id": "ea2d4bac6d74716b33f456dff3aae0cc0b43cca3", "job_title": "The-Hertz-Corporation", "place_id": "ChIJKbDEoXm_QIYRcRFBlp0dE8A", "address": "4901 Main St, Houston, TX 77002, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.483218, 29.7482286], "type": "Point"}, "properties": {"photos": [], "types": ["point_of_interest", "establishment"], "reference": "CmRRAAAADVATRkwqdFrQAacs195wxuJ1Pgo_NENxy2neRm6NolPRYbU4IVetHhen3t_hpkEIiNN8x397lB7ib30YsR-VszjaGWj8rQJ7mR3QX1xCnLSRxZgz_0Sb-k4lXX5MawwkEhCzVODwLZJ6rdlI3eWKph5jGhQJqjFl2bEO0nHjm5HdTd8QxSCX7Q", "name": "The Nature Conservancy", "rating": "NA", "id": "90af6fb9fb926dde9f7103577cebc4150bbb1dec", "job_title": "The-Hertz-Corporation", "place_id": "ChIJq-m4EX3AQIYRJkn4Lhccp2E", "address": "1800 Augusta Dr #240, Houston, TX 77057, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.42318089999999, 29.7345943], "type": "Point"}, "properties": {"photos": [{"width": 750, "height": 437, "html_attributions": ["<a href=\"https://maps.google.com/maps/contrib/106788706324997826205/photos\">Erika</a>"], "photo_reference": "CoQBdwAAAH5gPVjW_ZPOUdlcF83ITSM6my60Cd4bj-YTSQmauYh7FZQx4jaKlXhW40QAQr8ktstEcIYAjRGrkHFzo58UMlsfl72w_IfaFvyD6hb0TEqcfRKQIcwC1ghBULCiNJTyWiGCFZ3T-gYRuhy0NeK0xxgbVDzDYBe6Z4q6j8-Q-SUAEhD5Yo_r9rAyhyTOSphO3IGMGhQs2gVAMiDiVlQNICbgUr9u1TsI4g"}], "types": ["point_of_interest", "establishment"], "reference": "CmRRAAAAYQ7b5uR0WwQqXRUN6-HNvDg4AXPFhs8aVEZ-CKhI67aoJEKjarL3AYcLtL0kHcOvaarw28_NO7cu4wWc-3j7Ty_xU3ForL4NZFM8jJp5NgtqQ4rdrjb1iM7isaqEJnipEhAnR_3Z8zDTyaR0Eetz1okiGhT2PHA8Xf5a1UEAxdfjitTJOCMOnA", "name": "Student Conservation Association", "rating": "NA", "id": "1c5ea7722fc0d99e9f7dfca55f5d9078224d51d3", "job_title": "The-Hertz-Corporation", "place_id": "ChIJQcqBXfDAQIYRErawO-goGj4", "address": "2990 Richmond Ave Suite #400, Houston, TX 77098, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-96.038102, 30.055621], "type": "Point"}, "properties": {"photos": [{"width": 984, "height": 985, "html_attributions": ["<a href=\"https://maps.google.com/maps/contrib/110279808588468038448/photos\">Peckerwood Garden Conservation Foundation</a>"], "photo_reference": "CoQBdwAAAN41wTKw8Ubj2PnopMEp9SG69DbYeifLRoxC_WL9yuSyyyf47bLzKDHOyA7qdWRABhjh2gkIBCaWnzSzV0jTrtFRZcBRqh0RqUWfUjQ1hyPqtyXx31Gp6gJVW5yYSvvuPr5Fp7I7VvGx3balDQVBYQQB8YK3pqxPkHFiMkwVtKxlEhCMXfU9GO0FjtJ1HhNDBq5NGhSYuL_YSZyFLMI8RuavuFJ4b_eyng"}], "types": ["park", "point_of_interest", "establishment"], "reference": "CmRRAAAAaCOoifObvotQkxksLTGglAdjZb2xpeIVQ7bcTTBpZd0CxtZVs84fayIrqPogcL4tnEEbxAkymA0ccixclvIQdfh8vOedJ-1HHzpw2qDMjGFAiAzBV9bopyfWFUCcLh3nEhA7b1x33_7GMs3p4gqjpVSZGhSk5Ia_GTn1tXj-M1yqM7AAKpCcqA", "name": "Peckerwood Garden Conservation Foundation", "rating": "NA", "id": "e618a4c618cd67ce4f5fdc165f640220ab3b53b2", "job_title": "The-Hertz-Corporation", "place_id": "ChIJmUR7pvHKRoYRIIl0o73bPGE", "address": "20559 Fm 359 Rd, Pine Island, TX 77445, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.64386449999999, 29.7515036], "type": "Point"}, "properties": {"photos": [], "types": ["point_of_interest", "establishment"], "reference": "CmRRAAAAbhonTSo7P6Tg8XE4zVDVh799yJtmly1U0vDioQxXnN--8Pn8DrGl069EFNJ872qXK7c5ehFI6CPKyd9l0dSLb2vP2h448pclXta-zthhKx8rvao-3d7RYSetaz9WNZFnEhAmASqHrYle6VVLjA0i8wWqGhR0iZd6mb9iz0caqbUlCdfaUB7H3g", "name": "H2O Conservation Technology", "rating": "NA", "id": "30c07988ef8dfc62dac712b9d587daa4a36f2539", "job_title": "The-Hertz-Corporation", "place_id": "ChIJIWZRKeHKQIYRXxta3wOMGGc", "address": "1725 Hwy 6, Houston, TX 77077, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.5705632, 29.7714443], "type": "Point"}, "properties": {"photos": [{"width": 3024, "height": 4032, "html_attributions": ["<a href=\"https://maps.google.com/maps/contrib/108143329814504597326/photos\">State from Jake farm</a>"], "photo_reference": "CoQBdwAAADb_35bdvjeFHcfAtt4rSMw8_yAkat_wwyFIuD6TI2tV1rM4ZTPbQSc5QNI81BWYb33IDb09KgfEcdRsuEUGCfmapHLkX0xA-Jg1fvzAqN3yci42uqEgP1hQ_EDOgSU6rpOei_14tBHspWJW0xICAOQDAt23iErcLQXjPWDbtb_-EhAZLF2ZvLILp1sgF0eU_omaGhRSgdBIDwXip7iTut9tVHdPddARBQ"}], "types": ["park", "point_of_interest", "establishment"], "reference": "CmRSAAAAy2200g3vzPC2DyFID_XcTL0_8o2unif9pgbF1mQdLJ9l3kYKzfUZzreI7mGZYWnGRw3dopq0tm3z141P7oI6xulWBX4CcxdY1BBtaSoxb_Di4enDYzCnAWP6RV_2jaVAEhAXuLO2E3h_aoHOUwbaLBMUGhQpeH107XfbQwACI0gKB1HP9Qibsg", "name": "Houston Audubon Society", "rating": 5, "id": "050a5458d86bdd1cee7b09678bd6256d0a20a73e", "job_title": "The-Hertz-Corporation", "place_id": "ChIJlQOxwVDbQIYR2uX_TZl0TYc", "address": "440 Wilchester Blvd, Houston, TX 77079, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.56820189999999, 29.770778], "type": "Point"}, "properties": {"photos": [{"width": 1800, "height": 1200, "html_attributions": ["<a href=\"https://maps.google.com/maps/contrib/108765250995932379967/photos\">Audubon Docent Guild</a>"], "photo_reference": "CoQBdwAAADLko8ROxgNaLJT-6TC8PpQ43k5F7wMwxASp_8h28ewtdG_3i8WszMTW6QGO1ZF1FT_AK-birWVYRVofD77gnx2SMpMBMt2ngT-86LzMV5Vn6sepxLg9uSUMPa0QlawhMaxTz-lEALCHdib5mfJ0RlvTDnfe0Uhy0xlbEdUh8NO7EhA6WELen1-jfQDtrZi4LSrUGhT-6kZmjSfZ7gBTpbQkAdhZ4U3d4Q"}], "types": ["park", "point_of_interest", "establishment"], "reference": "CmRSAAAA63Ks_46gtH1UBHoZq1mA074YbSndL7zVW5zk5bB6v6zpj6S3IlpXQjnMVW-Lb6bpqYtC958aLml6uxWn8jSJ6KW9Q8CTBiFvgfdAZlKMO4RnQ-06r2emXPEH4iHoH57hEhCX33Z-rjwN8aErlyHI4F4SGhTsMoJgqjaFPV8uIfwIh7xlpR-pvA", "name": "Audubon Docent Guild", "rating": 5, "id": "7ddd5daf76cc4979e2ba6b062322d1c77d5d1c07", "job_title": "The-Hertz-Corporation", "place_id": "ChIJI9XyNFHbQIYRtwHb8EtTpeU", "address": "440 Wilchester Blvd, Houston, TX 77079, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.44932349999999, 29.7803218], "type": "Point"}, "properties": {"photos": [], "types": ["point_of_interest", "establishment"], "reference": "CmRSAAAA12WrzZ9_F4GU-PB9OtAGvZhyX7DctwyWNXBcMdXa0MQ9zvNJMtjjFMN5zJm9k4syGM18Zv_tA0Dl7hTMeM_CZ9XW-UqaBY-nqInrKnvhQGR6XqOAXfSqlWJVDaKFBCtXEhAat3OoY3zqZpjXqoXdLJpXGhQp_zFOzZFL9pnzdytF-CHzti01eQ", "name": "Coastal Conservation Association-Tx", "rating": 3, "id": "7258b034e119f31e82320bca6e72781ee9f79d75", "job_title": "Catholic-Health-Initiatives", "place_id": "ChIJcekacM_GQIYRPzL13cgQrPk", "address": "6919 Portwest Dr #100, Houston, TX 77024, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.47039, 29.655454], "type": "Point"}, "properties": {"photos": [{"width": 5312, "height": 2988, "html_attributions": ["<a href=\"https://maps.google.com/maps/contrib/101184977609161362375/photos\">aug4</a>"], "photo_reference": "CoQBdwAAAK6yfCUIUqME268OvgJVDqSRAYduUZq_AIu6zYc_vBsD3OZcF5SiZzWVpl2Ueim7WvoWDMblqD3oYJON-POXGdqhjj4Jylc5WB7Dqp4esefKgFCqLRl78h5t_YSPOsCAK6nUXCJPDl6zK-xMC6QZPHzcFfQSsAk3ecKP4-XCNc-LEhBA01kfht0zeA0x2z9hLd6UGhShj6SZXdSYb1Y42Qvu3tRwVq3bgA"}], "types": ["park", "point_of_interest", "establishment"], "reference": "CmRRAAAAAVCtlc866Of785ycprkWoVJjjIDNeLL0HXbjGFkoP44DI_1Uq2BedqxbUjMnZ-ncYfP2AUElktR-hwkJbgZgxeYlpRKNbu2FS4CM4LhwPm_f3FxeKLdzanyLHIYd4YJ9EhDo9gLLDAXK0RcNzFQcnMvTGhQ9phU8Ub5Rj9ZEZ9pZrXkvLmeiCw", "name": "Willow Waterhole Greenspace", "rating": 4.3, "id": "0127506e8071350c2d48f0ca56e939045297a0f4", "job_title": "Catholic-Health-Initiatives", "place_id": "ChIJR6_2zTzqQIYRsA7wExgfDWs", "address": "S Willow Dr, Houston, TX 77035, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.4003322, 29.7388505], "type": "Point"}, "properties": {"photos": [{"width": 1136, "height": 640, "html_attributions": ["<a href=\"https://maps.google.com/maps/contrib/117056878997299689379/photos\">Marisol Brown</a>"], "photo_reference": "CoQBdwAAADn_3xqN5U9FUb3Er5S1hhBCqJ-5d0muBKa1kfMnqVro2Uop_QEAobterJiH5361HK0fz0M-I8PVzzdKWNf9Bqo0L5OcoTYHTFkY0BfuUpn3TKm949DDInM5viGDgQowPqrlRbMx2LCakuNqaNYzUlqy1NHnk85G2IaeQp_qqq1VEhATDNXwCEEYnuyJtAPK4tbQGhSFDGXCajb2IjEXmXT0i_E-PWjJoQ"}], "types": ["point_of_interest", "establishment"], "reference": "CmRRAAAAClqDq3cUXcqJv4N9Hxdtu7vNKdGnZSX2PE4ay6eNw4X0WPVzak7S1_YmG5gKlzVXn1ethEBwUwnK-3z6VFFuPyy8pZSrfvZin-LmCS4N71Bk2OygrlawVMEy4iA9lnUjEhDKatnRtpzuvoEE5YAiyeU-GhTIckAB5OY2Pdnw3fatJV5C4O-hPw", "name": "Masters Fine Art Conservation", "rating": 5, "id": "a462c2eef4e22ea319485ae7b84f3d20756cbdd1", "job_title": "Catholic-Health-Initiatives", "place_id": "ChIJp8u2bZvAQIYRbosnWz6cVmY", "address": "1612 W Alabama St, Houston, TX 77006, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.3876169, 29.794149], "type": "Point"}, "properties": {"photos": [], "types": ["art_gallery", "point_of_interest", "establishment"], "reference": "CmRRAAAAk-6kAGwID7Pi3rT2LoifZnFErIyVSdSKCMthoqc0pZFx05FbAi_RasnVQCYqES0CRk-eeJ2sL6n7x8B9ySVvolV8iyPvP2FvePyBE270CRBUaqFDA7N87CQYiXBf2q4sEhAqomSViS7xY841IRNdCmceGhQfjNZBcbIZfO5cKVTLAp8ICOenyQ", "name": "Whitten & Proctor Fine Art Conservation", "rating": "NA", "id": "883a8c5ef35ab28e1630235ad65a6b16506a67fa", "job_title": "Catholic-Health-Initiatives", "place_id": "ChIJ8YuXE6K4QIYRn1SF1hazFEw", "address": "1236 Studewood St, Houston, TX 77008, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.3858767, 29.7300997], "type": "Point"}, "properties": {"photos": [], "types": ["point_of_interest", "establishment"], "reference": "CmRSAAAASSU_CFXB63r0yPjzVFvXe3XU3L7aEKhhTVfc86b7npTB4GHBesGP-Vsa6QGaOF99qCT0o3l1hwJa-o-1KmEGZHgp3lWlsqcjmno-1jFP2RbcTVbWOPOCyVQwFbysDYkwEhBzMy6yJ17EXLs908qLAa1CGhTzP5tHE9DvluMvkWOKVuUR9yE7qA", "name": "St Mark Fine Arts Conservation", "rating": 5, "id": "ea2d4bac6d74716b33f456dff3aae0cc0b43cca3", "job_title": "Catholic-Health-Initiatives", "place_id": "ChIJKbDEoXm_QIYRcRFBlp0dE8A", "address": "4901 Main St, Houston, TX 77002, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.483218, 29.7482286], "type": "Point"}, "properties": {"photos": [], "types": ["point_of_interest", "establishment"], "reference": "CmRRAAAAlblsKXwEO3tBS_vdnyxDup2U_K068gTr3C53QMmAUUcAD5YPhlI2Cj7DiTE57O56G1NpFaM5mNgiT_zbuKFW1bDursIAFwZ4xHgisg96dCODtiz7xYxR0E-r7ExAAIqeEhBkJxbIHSkse5QnvGn23yccGhRBc7m8ipIZQdeQhI_oFgUp7mzv5A", "name": "The Nature Conservancy", "rating": "NA", "id": "90af6fb9fb926dde9f7103577cebc4150bbb1dec", "job_title": "Catholic-Health-Initiatives", "place_id": "ChIJq-m4EX3AQIYRJkn4Lhccp2E", "address": "1800 Augusta Dr #240, Houston, TX 77057, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.42318089999999, 29.7345943], "type": "Point"}, "properties": {"photos": [{"width": 750, "height": 437, "html_attributions": ["<a href=\"https://maps.google.com/maps/contrib/106788706324997826205/photos\">Erika</a>"], "photo_reference": "CoQBdwAAALBz06TzoO3bUURbj6Dkq4iL8Qcsw4M-tlxVU0dEh0D0xFXwAi0R25zWIaKa8z-GxM8ipBJdwwxJZEj9Q6a7uUsf8SonWsi1Edtv5dGNdm2Irt2bTULdwYQrluI8y_-ygI-46eDUbqCNqbcJFwBYX2Zt-itDH9shOy5JbkGByxZGEhAPDcWC-DNoD8Koi_IVjSOFGhRA5_RQ05Kt1S3gVXSUARnfGccF3w"}], "types": ["point_of_interest", "establishment"], "reference": "CmRRAAAA4AQs5O_1HkEa658Wn04yPLoiKdATUCpOs_sEme0MsQK1FDv1eFlnPDcFweEiE_fPqXuCNDdklH9JUL1-5rqhCOFZW3Kn8zU1vpML9X5pllZgb-XeClOx8lBPpNoWVys6EhBJJr0LvEhJ-8pAhpq9F2-BGhQw-IFOHd-gcsKzsqHu8ikWdRBjcA", "name": "Student Conservation Association", "rating": "NA", "id": "1c5ea7722fc0d99e9f7dfca55f5d9078224d51d3", "job_title": "Catholic-Health-Initiatives", "place_id": "ChIJQcqBXfDAQIYRErawO-goGj4", "address": "2990 Richmond Ave Suite #400, Houston, TX 77098, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-96.038102, 30.055621], "type": "Point"}, "properties": {"photos": [{"width": 984, "height": 985, "html_attributions": ["<a href=\"https://maps.google.com/maps/contrib/110279808588468038448/photos\">Peckerwood Garden Conservation Foundation</a>"], "photo_reference": "CoQBdwAAAEpay5tVlbmpsGvE-FQgpmTLAhDD3ItqbwnmGtN0KNCQU8tnDvbHTn7wD4NZeNT4Wds2gwYOR6oklPfhd5hL4U5K0MmTEjt5P3oUcyRrBeHH-3knrdxD4DlurpPMW7dFFZx6O8GNBcyzGRvsbVDNxADoj0x5jyxw7A4j8rKplTFbEhDSnzawETdT1NZ0wE-jzHunGhTxyRGQ9QhXhjy0XNfFhQLSYTypHA"}], "types": ["park", "point_of_interest", "establishment"], "reference": "CmRRAAAA5v77b4vEn3t8kdZAQDpkhRQTnKU9V-lkBrn-5eGVLQlvNySGzgK9M92IqUEoySKVMeC10IMQ5p_2ju5kxYLn91kM1jM3R73rxL8I11jzhzo8deHi41QlFjU_d9o2i_89EhA4cUm8NVsGQRKQP1yjuRxRGhSWXGw_nIMsITKj0Txm-AkEO-fGaw", "name": "Peckerwood Garden Conservation Foundation", "rating": "NA", "id": "e618a4c618cd67ce4f5fdc165f640220ab3b53b2", "job_title": "Catholic-Health-Initiatives", "place_id": "ChIJmUR7pvHKRoYRIIl0o73bPGE", "address": "20559 Fm 359 Rd, Pine Island, TX 77445, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.64386449999999, 29.7515036], "type": "Point"}, "properties": {"photos": [], "types": ["point_of_interest", "establishment"], "reference": "CmRRAAAAqpazV6V6Ndvadofe-QZCDdN9dcL2DQnmWOjeInRL2jpfLya9G4iM8CmSOoR_bTocqsccWZb9jyPKFKSdJ2sruYbxErZaGwmjNi8ArfJlk0XuNOVEKVNjLioytYuxPmjaEhD-G6_MGqWqaCBNVMHu_5kpGhSKrPAVYFZIz4GegEOaLhf-xDtJYQ", "name": "H2O Conservation Technology", "rating": "NA", "id": "30c07988ef8dfc62dac712b9d587daa4a36f2539", "job_title": "Catholic-Health-Initiatives", "place_id": "ChIJIWZRKeHKQIYRXxta3wOMGGc", "address": "1725 Hwy 6, Houston, TX 77077, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.5705632, 29.7714443], "type": "Point"}, "properties": {"photos": [{"width": 3024, "height": 4032, "html_attributions": ["<a href=\"https://maps.google.com/maps/contrib/108143329814504597326/photos\">State from Jake farm</a>"], "photo_reference": "CoQBdwAAANTvxIlScAr8Z_HfiEXkYbrrYlnMlyJKkRGDMVsICpEfvx5q89xtKKICYRmu425L0--CXqOtp5Kv9I6-EQ96o_5kyfBn0Vdo8wbQWPIxwzXNSVArjtrELdZ497aKeh34gJBDLZI0VlSMjc98HOC4WBAhhxVtOQi0-tvnDOkVgwUDEhAdv387rkORY29gUetRXIKIGhTCtFfjZifdoP52tdyx14Iw4hkg9g"}], "types": ["park", "point_of_interest", "establishment"], "reference": "CmRSAAAA-T0DtvWr6eOeFKYbij3eljj_bJPMwDRZ1JCT7YY7hY2-um63gkQK9LAnElDFXBtk3voUgNRpTl-HGt2NUQzS5fi5Fz_tkq4EwXdo-iuCXnf5V0ccQmsqRJHw4GUkaohQEhC9fz26upEbKV-Yvk-dFBbcGhRM9VwdZtqX346gDmairy2f_phQGQ", "name": "Houston Audubon Society", "rating": 5, "id": "050a5458d86bdd1cee7b09678bd6256d0a20a73e", "job_title": "Catholic-Health-Initiatives", "place_id": "ChIJlQOxwVDbQIYR2uX_TZl0TYc", "address": "440 Wilchester Blvd, Houston, TX 77079, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.56820189999999, 29.770778], "type": "Point"}, "properties": {"photos": [{"width": 1800, "height": 1200, "html_attributions": ["<a href=\"https://maps.google.com/maps/contrib/108765250995932379967/photos\">Audubon Docent Guild</a>"], "photo_reference": "CoQBdwAAANCJFuHHeboCVc3McfRsqMKikJh5hRZjxaxpzUFuAd1dGDrK5jG5PXKoQRcN9_lbCnjMCw_ozD81prgkjT9rw_fnWBzKxPYtHZt8k7KWFeLkTsHo32bILZ2zJNqK2WVmlhQII_5i1MA7yqX1tqqH_GZN2766T0VPUL4sP1xcnVSVEhAwMZm0tcsTKTys3LcPmoorGhSuY-kQzl9v_YThidPd4JI139--Fg"}], "types": ["park", "point_of_interest", "establishment"], "reference": "CmRSAAAASdplSsMtyOIMwlNTm6ELf1dkmIK0QFOUfo2CajnDSjAikSuFQMlQx3WAzYPuF64H5nzeh-C6qV2ti6Pp2xcBUMUscN6brZvscXlzEYVhgmPfwGSARzo_OHo-eSTa0G5_EhCkBZgxAPqfBRsZB1qmtDSuGhRa83AKFjlmR9MO1HullT0JKH2ATQ", "name": "Audubon Docent Guild", "rating": 5, "id": "7ddd5daf76cc4979e2ba6b062322d1c77d5d1c07", "job_title": "Catholic-Health-Initiatives", "place_id": "ChIJI9XyNFHbQIYRtwHb8EtTpeU", "address": "440 Wilchester Blvd, Houston, TX 77079, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.44932349999999, 29.7803218], "type": "Point"}, "properties": {"photos": [], "types": ["point_of_interest", "establishment"], "reference": "CmRSAAAAT44wLFVBqXQCPHQBiHeQVvDDsIw98IGZkGp2Fslk0dRAOWOsCvjQIQpq_HpfjkwTe4sKBqLxNqfPgCOCjSTvAM6seuOtfJeNhbM5qGy9Ha-_7TnPZvbIldMNkorwrgFoEhDlJuIbeD4634LYn8WVpq0RGhTJCIDY_weXyos0PZ5_1QV0ZbIbmQ", "name": "Coastal Conservation Association-Tx", "rating": 3, "id": "7258b034e119f31e82320bca6e72781ee9f79d75", "job_title": "Conserva-Irrigation-1", "place_id": "ChIJcekacM_GQIYRPzL13cgQrPk", "address": "6919 Portwest Dr #100, Houston, TX 77024, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.47039, 29.655454], "type": "Point"}, "properties": {"photos": [{"width": 5312, "height": 2988, "html_attributions": ["<a href=\"https://maps.google.com/maps/contrib/101184977609161362375/photos\">aug4</a>"], "photo_reference": "CoQBdwAAABja00ru3Orzx8kr_mHJmGtu1Or7Oi_Y-W6gEUQbl78bOoRJMmwVWm4-C6XvZtn44UF9iy4A59eOjMvV6j7LVawr5_xvnqhmFteuc7Cu6afXBBT00uNwFtL1IqRKcANSmyhsExsFHdo-RQEjPrEBEtDuo7a82HbPU6Sy9RSIyUr8EhD60nCyBViNGqOHbbhyUyVtGhTNLgsbAiXeF8t54DvqBsGfsclUJQ"}], "types": ["park", "point_of_interest", "establishment"], "reference": "CmRRAAAAliwdg-FK-xZSOlVx4rf9NvBKoASS2affdhIsmrpkhwnKZnHSq5rzejQvXohPIxA3ASXB0lYG85sFXx9Bs4sWtfTknIrykZBBJPrbZuSteYmPfCxIGfEbiDcsiA2JG2TBEhD_4ERqbqRGCR8JcoFK4yXMGhRDSqoKVM39iQQLDXdUIvHYdnGKUA", "name": "Willow Waterhole Greenspace", "rating": 4.3, "id": "0127506e8071350c2d48f0ca56e939045297a0f4", "job_title": "Conserva-Irrigation-1", "place_id": "ChIJR6_2zTzqQIYRsA7wExgfDWs", "address": "S Willow Dr, Houston, TX 77035, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.4003322, 29.7388505], "type": "Point"}, "properties": {"photos": [{"width": 1136, "height": 640, "html_attributions": ["<a href=\"https://maps.google.com/maps/contrib/117056878997299689379/photos\">Marisol Brown</a>"], "photo_reference": "CoQBdwAAAIZLUkTomRZAe3h7-_DvsDXKeLoZbpIgsaU4NxMsEFl9-xFEPq0fXvlZi-0PqctEyJVALEKbgFhdJWjJEq3ZjB6L_K19eJCP7JeY8TqnT2kGCoxbBTxYHPH7GTt3AslPEhdxdYDcMfGq8rGO5ONOYu9SuZiA90CSXiGZBEeXL_4FEhCd37IhgQjk2G8MUdt9KWbOGhQN42aCGaeUQnfNKYJ66AQYMXBBmw"}], "types": ["point_of_interest", "establishment"], "reference": "CmRRAAAAf6XJDibxaMBXQ5-_D3lemntfS0ACRd7UTTbUP0UiNOPxVktO1bYj959itNdH3cMLoJLbgNyEz-LgeK3VKfmDDwemhdKn_HxIJzuY7UqbDqzryUtxeWXxx6o-JzdiGmluEhAC2If_AHAzUO7OcxhT_AxgGhTenHarjDX11m2YaONcHzkVDJRHMQ", "name": "Masters Fine Art Conservation", "rating": 5, "id": "a462c2eef4e22ea319485ae7b84f3d20756cbdd1", "job_title": "Conserva-Irrigation-1", "place_id": "ChIJp8u2bZvAQIYRbosnWz6cVmY", "address": "1612 W Alabama St, Houston, TX 77006, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.3876169, 29.794149], "type": "Point"}, "properties": {"photos": [], "types": ["art_gallery", "point_of_interest", "establishment"], "reference": "CmRRAAAAJsbewqkBCEwoZDVw-4WQQfJslDbn0T6dK3VtJsIRxX7vU08C7JHAM6v3xpVn5I60uHJzAs7sq2FWuXlCb88rKuvWXyz_CCAFQXyRNNtdn6u-Z-ZitpyjXUQ2LvjCYUQPEhAZzf3Ok7-j3ES-Kq2VsJKDGhTi3tOfimaCo8vvmT7Hu5VKE1_aQg", "name": "Whitten & Proctor Fine Art Conservation", "rating": "NA", "id": "883a8c5ef35ab28e1630235ad65a6b16506a67fa", "job_title": "Conserva-Irrigation-1", "place_id": "ChIJ8YuXE6K4QIYRn1SF1hazFEw", "address": "1236 Studewood St, Houston, TX 77008, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.3858767, 29.7300997], "type": "Point"}, "properties": {"photos": [], "types": ["point_of_interest", "establishment"], "reference": "CmRSAAAAKZkL90PwZ1JVx40fmWSPl-UB9UasvddhTd66HjHFM0i5lfMauBdWa8xE0X3UChe4upe7WxBd6F6aD3ag6rWrqfZ-3atxzFyKPafr2mOnvYPmQwOdYERFa1UZZqjevBRcEhAaSzzVciMigs7TBcv_eAjaGhRYwFcEFMjhEVdXHf9UxFIORtE0XQ", "name": "St Mark Fine Arts Conservation", "rating": 5, "id": "ea2d4bac6d74716b33f456dff3aae0cc0b43cca3", "job_title": "Conserva-Irrigation-1", "place_id": "ChIJKbDEoXm_QIYRcRFBlp0dE8A", "address": "4901 Main St, Houston, TX 77002, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.483218, 29.7482286], "type": "Point"}, "properties": {"photos": [], "types": ["point_of_interest", "establishment"], "reference": "CmRRAAAAIOlu834_8ceTo-uj0b34zUm6SB79qzd0AlkUjIwJoeUfvHzurZEXOvbnmzsMgKnTDIc8s3kgDAZWuvbFjUP1jT9v349MDq5QSCXSivfQ9H9oeWXnKUpYJ-Ha-ByR0wNPEhA0t_3Z3R2UyNJhDo12vClfGhSFH9r2wrKTVdW5bEenWbGZ4QOv_w", "name": "The Nature Conservancy", "rating": "NA", "id": "90af6fb9fb926dde9f7103577cebc4150bbb1dec", "job_title": "Conserva-Irrigation-1", "place_id": "ChIJq-m4EX3AQIYRJkn4Lhccp2E", "address": "1800 Augusta Dr #240, Houston, TX 77057, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.42318089999999, 29.7345943], "type": "Point"}, "properties": {"photos": [{"width": 750, "height": 437, "html_attributions": ["<a href=\"https://maps.google.com/maps/contrib/106788706324997826205/photos\">Erika</a>"], "photo_reference": "CoQBdwAAAGXAF6kfSXt2V7Wrhm9ItJChFZW_3y1nLVjo2TUjZfit-vay4d8nALpqLrPghkBm2Li1johb0bQzB6iGhHSFyUuIn9EH6nHvGZTHgx8NRVCGQbciaW3xwCm6DQPZbi_Y38putGaGeEBP18RlpL7YbQKjuvlRr1Svb7VZgitkdB_1EhBkmQGw1ObxlACxJg9_u6YmGhRuJcWMAeIjMEDcaWlzCFVMkFnrAQ"}], "types": ["point_of_interest", "establishment"], "reference": "CmRRAAAASnzHqm8UOvaxtxLgN5OFwO0qwtNj6gbgdgSP2tMnFBT1m_7dsbtA_AoHE0UMa07o84MHdkKFG2eCHRQgKwxbSrDKufYoWLLhUOHYtJ1fAymqKmMGRni9X4C46vhcZA8TEhCiNNFKlAIH2B6E4HSGIdWFGhSFhsNF6hMbGPlNSYoc62xBgWrWrw", "name": "Student Conservation Association", "rating": "NA", "id": "1c5ea7722fc0d99e9f7dfca55f5d9078224d51d3", "job_title": "Conserva-Irrigation-1", "place_id": "ChIJQcqBXfDAQIYRErawO-goGj4", "address": "2990 Richmond Ave Suite #400, Houston, TX 77098, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-96.038102, 30.055621], "type": "Point"}, "properties": {"photos": [{"width": 984, "height": 985, "html_attributions": ["<a href=\"https://maps.google.com/maps/contrib/110279808588468038448/photos\">Peckerwood Garden Conservation Foundation</a>"], "photo_reference": "CoQBdwAAAHEZP6sKcsiu8l5G-CNXunyxOJq89faNqZawFZmGk7gjv9FCKhUpbs_J1jCDhiYfA2yR2x_o3p6iIyjNiTUG6nlroN3qW2W18U80lId1goGgdyh1j6BZkimZ3XUvify7eyXqTAjflkA5Kim2P1foZ-3WBssdkGSgZS1Q1ebINla7EhDzB4ss0oEeXw4RIcrin05tGhT1sVM38Ut9nbPaBb-tf8jd2xGnxg"}], "types": ["park", "point_of_interest", "establishment"], "reference": "CmRRAAAAZvQqL5_pDHn2CKDNSfymnQvS0wc4_p4AnRWsDzf_8_X9ZACweko1mMh7xBUViegdQVY-oZG0gbGhC4Q4Nyl0La6CO4dWnse8tOyl8oz32kdOZsjeTMhWkdPL-bNpQsDiEhBeuGLP01nRG6Ko55qOH9fUGhSQmKgjfAqel4syju32mWDk70z1ng", "name": "Peckerwood Garden Conservation Foundation", "rating": "NA", "id": "e618a4c618cd67ce4f5fdc165f640220ab3b53b2", "job_title": "Conserva-Irrigation-1", "place_id": "ChIJmUR7pvHKRoYRIIl0o73bPGE", "address": "20559 Fm 359 Rd, Pine Island, TX 77445, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.64386449999999, 29.7515036], "type": "Point"}, "properties": {"photos": [], "types": ["point_of_interest", "establishment"], "reference": "CmRRAAAApDHVW4feAiT78eieDcgRvOQo9lu6-5dJm3JfYZVaOefbN7Ikr95IPQba_1P8m0IOiscgYzU6dXnme28DZYR0tAMLb9Kkt5nNLSPwnq7fcORq4Ju6RhqlZNfPDjpQ80FtEhBZ-GXobemGdEZT-p-cq28dGhSXHMB5P_QdVyB7189CwlAbsOqOKg", "name": "H2O Conservation Technology", "rating": "NA", "id": "30c07988ef8dfc62dac712b9d587daa4a36f2539", "job_title": "Conserva-Irrigation-1", "place_id": "ChIJIWZRKeHKQIYRXxta3wOMGGc", "address": "1725 Hwy 6, Houston, TX 77077, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.5705632, 29.7714443], "type": "Point"}, "properties": {"photos": [{"width": 3024, "height": 4032, "html_attributions": ["<a href=\"https://maps.google.com/maps/contrib/108143329814504597326/photos\">State from Jake farm</a>"], "photo_reference": "CoQBdwAAAFz71ki_D2v4Wc5OosUyi3EdiutliQ9ec-ufTuEw6h0EhivLyBrJyltbkLTRQ5luc__fxKeSZqIvuPAm0zUJmSi5R_nUNVxRW61cLLfpaMWU4zAonD87q3onx95nHCaF3ENMHmPoswSLDz9cBqPVQTDHyMa5kgNehY47HNtuUdViEhCPthgaeR3SSlnveHufi07fGhTLiJk4WrFSof2mA4Tmn4cNG4OQfg"}], "types": ["park", "point_of_interest", "establishment"], "reference": "CmRSAAAAdxYLWXjNH2nskEzzn8ORrv1Ci_2qo29gVGuxYlgY7NKA1L-nclfMlKywgHm3nX6ArxWQCvralanVFv0ipezgbrkYyDjAuBcBC7dF6A99YsSF831APvCROwZpNqvbIjubEhA_d1TaPj96KQLvIESHteRiGhTXYAYCEl7T3s072tm7zy93cIb6cw", "name": "Houston Audubon Society", "rating": 5, "id": "050a5458d86bdd1cee7b09678bd6256d0a20a73e", "job_title": "Conserva-Irrigation-1", "place_id": "ChIJlQOxwVDbQIYR2uX_TZl0TYc", "address": "440 Wilchester Blvd, Houston, TX 77079, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.56820189999999, 29.770778], "type": "Point"}, "properties": {"photos": [{"width": 1800, "height": 1200, "html_attributions": ["<a href=\"https://maps.google.com/maps/contrib/108765250995932379967/photos\">Audubon Docent Guild</a>"], "photo_reference": "CoQBdwAAAPn1uugvpBXRz0nj-g_MS8CZ9WP3Yrn6hBlPZPPi6UNIm7YimAg5eTEh0tV0pdT1bFoD4UcbaSF5oD192GwxoX8agTJpP22IjvWrf0_xyC4qJ0b1fFcZ8zPRLhbdfFZ9XN7FOly2G8Ozdx3qyVVka-qBDYxYz_2kqiXss1LH45p0EhBwAqYsK0EsAq2UNt1uRhxMGhTQEIn84jtT-5E2RzPP6RFd34_8rA"}], "types": ["park", "point_of_interest", "establishment"], "reference": "CmRSAAAALJsPR3tmcUQZ8QFCAsFI5I9A8qWFcqJXoefWJe2oRlQkSa9wm6gtF14x_Emd2QXZQWkNXnt54eXW2PRFADiEnIMrKUDeRGSnjApfYLihhVQ5YscAF9LDbEaagmllCLibEhB0BsK4DyblTFM5gAWcQBqRGhS83wLodo17slAU-qZndGJnR10Otg", "name": "Audubon Docent Guild", "rating": 5, "id": "7ddd5daf76cc4979e2ba6b062322d1c77d5d1c07", "job_title": "Conserva-Irrigation-1", "place_id": "ChIJI9XyNFHbQIYRtwHb8EtTpeU", "address": "440 Wilchester Blvd, Houston, TX 77079, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.44932349999999, 29.7803218], "type": "Point"}, "properties": {"photos": [], "types": ["point_of_interest", "establishment"], "reference": "CmRSAAAAliyA4PdoVnclyath-dbqUKspsoMlBDpbTl-Zek9Ng1PTICYMoiyObaPgOdudcCJVG7UGmDQK8t65jfEzgNfxnOH-1knNOovTppYTRlIUqJ5DA3AQ05ATc6pociz8dBjAEhDuF4UqtTdKIpJuJrCJOufKGhT6kqGJcUuTOZ75kEnrv9rBf-XoRg", "name": "Coastal Conservation Association-Tx", "rating": 3, "id": "7258b034e119f31e82320bca6e72781ee9f79d75", "job_title": "Yankee-Candle-Company", "place_id": "ChIJcekacM_GQIYRPzL13cgQrPk", "address": "6919 Portwest Dr #100, Houston, TX 77024, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.47039, 29.655454], "type": "Point"}, "properties": {"photos": [{"width": 5312, "height": 2988, "html_attributions": ["<a href=\"https://maps.google.com/maps/contrib/101184977609161362375/photos\">aug4</a>"], "photo_reference": "CoQBdwAAAAImBz6bkx8dUd2Qrt75jmSv5YecVhcfzo4zV8QXZ9fAJXOZaMusExtCGWWaWLGxzvG3w12Kf2YCIVPc2GlosZt_LlHRgvZV_Qkrh0NXnSi5oNvb6iUdUlLGiA-PWZ5xEsmYYV_PV7zP-NKrtJOT8qUPDSkllIL6jJ39zo8_5NiXEhAXiMcOFL1Wnk6dSGXuQL0rGhRRm_AD7oIivqlyqrv3LjtO5PBKVw"}], "types": ["park", "point_of_interest", "establishment"], "reference": "CmRRAAAAgwFB1yKeKiQCLwswJkQb-XrNTORRu41PdchuzH1D8hjZE-bW640gERVZTttvf6zPWiNq4cI93DWXUMSIv5udjGZJdB4DarY3LEGxxK11-hxBcJfahKq253G1PgsRy-hWEhCX85wbBO6KdkzJQKo0gdGBGhR3mrWQMiamoY2x9eLjwLneRtHK6g", "name": "Willow Waterhole Greenspace", "rating": 4.3, "id": "0127506e8071350c2d48f0ca56e939045297a0f4", "job_title": "Yankee-Candle-Company", "place_id": "ChIJR6_2zTzqQIYRsA7wExgfDWs", "address": "S Willow Dr, Houston, TX 77035, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.4003322, 29.7388505], "type": "Point"}, "properties": {"photos": [{"width": 1136, "height": 640, "html_attributions": ["<a href=\"https://maps.google.com/maps/contrib/117056878997299689379/photos\">Marisol Brown</a>"], "photo_reference": "CoQBdwAAAJol4XTSj0X1tAe4aYNeN9Tf5uYV47m0Gu9Oop8xAmPmAleTfQgg8SFe6ZdJ09BdjoZPrR4RKr7AKZwrUQAnvHuS5qcbKKmslfF5AuiMNmb31YFfX1LgVrK-N9s4oI_KL_C1ZopgmEUsIyPWsh184s8qHarjwB9HFfljFrFPBP1GEhBnr8QyLnDfZ7hCvCzoRi68GhTDYsEKjHSGgP76fcxlmHdpYczI4A"}], "types": ["point_of_interest", "establishment"], "reference": "CmRRAAAAy9R6PiF25KUgpq9Wm3yY0DkDwi_JzXCsdp_5lE6X7a_bKZEpMYVC7SxJ3c4DRyV3uLSMT94kEkono13FumQBPtz0BV4jPbucfRdLCp9I4VVrwzwd2LuNnE7B9iZu-1INEhDsu1xdrPMXvJI6gACQYtdoGhQZ4oFvb1jyOkJIB4GNtAqhdfSejA", "name": "Masters Fine Art Conservation", "rating": 5, "id": "a462c2eef4e22ea319485ae7b84f3d20756cbdd1", "job_title": "Yankee-Candle-Company", "place_id": "ChIJp8u2bZvAQIYRbosnWz6cVmY", "address": "1612 W Alabama St, Houston, TX 77006, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.3876169, 29.794149], "type": "Point"}, "properties": {"photos": [], "types": ["art_gallery", "point_of_interest", "establishment"], "reference": "CmRRAAAAq0BSP2uZO40bM5Y7aQL_dYhM71djzlKRbKDGn01tpOcjnfAeXZ_ezWAtIEPScHsrXCwuqNlU_23Uc-gtAzcJeX-KklBgjt2B9ORQ4mFNyJ3YLXpgxSmjlRcld8w9V8e1EhAmMCRvxPx-Gc-bXuyY7fWKGhRSV3mnbUh98vSP5C04fHHrQ9sMNA", "name": "Whitten & Proctor Fine Art Conservation", "rating": "NA", "id": "883a8c5ef35ab28e1630235ad65a6b16506a67fa", "job_title": "Yankee-Candle-Company", "place_id": "ChIJ8YuXE6K4QIYRn1SF1hazFEw", "address": "1236 Studewood St, Houston, TX 77008, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.3858767, 29.7300997], "type": "Point"}, "properties": {"photos": [], "types": ["point_of_interest", "establishment"], "reference": "CmRSAAAAHvEED5hc_DJjlbihfZEMZBVX5Uag9OyA-6oSAwN1EUZrfTW15ZqkBr1raPe9HX0u0EaTBAhW_C8UiJlRo6ZrV5-5J9hPe08AWd5LADM0UkBemwfZ1G-ZBCEs0w6u6OuqEhDtatDMChpK51ScYHWd9ZTBGhTxLVt3Ok7t242vaXHekXCXUx0wSA", "name": "St Mark Fine Arts Conservation", "rating": 5, "id": "ea2d4bac6d74716b33f456dff3aae0cc0b43cca3", "job_title": "Yankee-Candle-Company", "place_id": "ChIJKbDEoXm_QIYRcRFBlp0dE8A", "address": "4901 Main St, Houston, TX 77002, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.483218, 29.7482286], "type": "Point"}, "properties": {"photos": [], "types": ["point_of_interest", "establishment"], "reference": "CmRRAAAA53hZYDGMiThW-LAnb7uMlhO1_6JfucTv3Q78dkGjX7EBEtLmykXsvQsHy1aLM24s9W4B0cdFSH6G8bunmSkWF9_3EdNRObPfa3e4ZaRqMANneI1m-t22Yr2U-sOVAWGUEhDzKuZgyYIws1wwtXykzmrkGhSI9ZGAHJT8e7CqEOZcyVSVEvxA0w", "name": "The Nature Conservancy", "rating": "NA", "id": "90af6fb9fb926dde9f7103577cebc4150bbb1dec", "job_title": "Yankee-Candle-Company", "place_id": "ChIJq-m4EX3AQIYRJkn4Lhccp2E", "address": "1800 Augusta Dr #240, Houston, TX 77057, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.42318089999999, 29.7345943], "type": "Point"}, "properties": {"photos": [{"width": 750, "height": 437, "html_attributions": ["<a href=\"https://maps.google.com/maps/contrib/106788706324997826205/photos\">Erika</a>"], "photo_reference": "CoQBdwAAAA7mVxjJygWtHe_Stge7_5Mp8u59fXk-6prNM0kyoKPzJQMOOXxtKNo6lniC-tqp7aZ56TYHihzHdZa_7yOpsnMKWjlWBpO2BnotRnqqmqz6_1q4qCWvphe-CHXO8zArTDdpn7TGBQ4KTk7-SL-P4WR35uf9zaH9RFomLk0J-HuPEhAK2ADf-VbSAWrq-9sSoG_EGhTIdKSP04g38XLcq2YWiQOf4OTtbA"}], "types": ["point_of_interest", "establishment"], "reference": "CmRRAAAAqOwSbrpEUtynPrhyFSnHft99pl8kX5mby8W29naO1ZC4nDKtQQTx6-dbaKPlbMaaKi0dkS6inCgiOWmuhdRtCxIKz8_0tgb8hBEi17QzulUXI60yCR-9Yv_rS4HVqnYNEhBL5eWzHc1ARB82N06wZXJeGhRB70tPt6Wt_hgFUgfbc6AJro4WIw", "name": "Student Conservation Association", "rating": "NA", "id": "1c5ea7722fc0d99e9f7dfca55f5d9078224d51d3", "job_title": "Yankee-Candle-Company", "place_id": "ChIJQcqBXfDAQIYRErawO-goGj4", "address": "2990 Richmond Ave Suite #400, Houston, TX 77098, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-96.038102, 30.055621], "type": "Point"}, "properties": {"photos": [{"width": 984, "height": 985, "html_attributions": ["<a href=\"https://maps.google.com/maps/contrib/110279808588468038448/photos\">Peckerwood Garden Conservation Foundation</a>"], "photo_reference": "CoQBdwAAAFGElP-nw6X--NH-WLmAJFPm0nC1ErpAK7QGJkTCPHbXUtraZJYZOGAHMjW7hSfRVQhU1984hgHcLZlE_oT2VV6PJ-Df28ToD6tg1ea8HXRsX5rXjui9YJz0b040-zSnJShhZUJknUtTZ1jgTisXLSrVv8S-jSI4PhmzInySajVREhAv29qCip12k9m9RJaD8kK1GhRLx_cDteIK1LIkppqP5mQIOxFB7Q"}], "types": ["park", "point_of_interest", "establishment"], "reference": "CmRRAAAA8Hg7mrcSvV2m9-67ZgPsTOBzyKXVs2QDtRpSrvTfbU99fZDRFSoMOUJy_msjT3pxVOiKNyv4HF6N98UK9_YuEUWi7myVqLl5JQ1z_D0jX1MklGT_mkfKj7SHBD_4AdShEhCV0p5n5KRGhI52QB79VD5KGhTmRVjozKaOJt_8JzkjX01WRQMb0A", "name": "Peckerwood Garden Conservation Foundation", "rating": "NA", "id": "e618a4c618cd67ce4f5fdc165f640220ab3b53b2", "job_title": "Yankee-Candle-Company", "place_id": "ChIJmUR7pvHKRoYRIIl0o73bPGE", "address": "20559 Fm 359 Rd, Pine Island, TX 77445, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.64386449999999, 29.7515036], "type": "Point"}, "properties": {"photos": [], "types": ["point_of_interest", "establishment"], "reference": "CmRRAAAAXIxNCc0FbNFdFlcOin-ryU1VMhfBATXnhTxXqGyZwJGzNru-8BlS92IBIfiCcRFKxXn6BbiJcrD3BuvPEAzGTeUTnXAMETeCfBOSpqoBbdLKRML0hclz_MUtl0cT6yi1EhCjVpmjkfMZwnpR2R0TJK-LGhTW-7O_GuWKcAMgrgXCaS5tb2_Gsw", "name": "H2O Conservation Technology", "rating": "NA", "id": "30c07988ef8dfc62dac712b9d587daa4a36f2539", "job_title": "Yankee-Candle-Company", "place_id": "ChIJIWZRKeHKQIYRXxta3wOMGGc", "address": "1725 Hwy 6, Houston, TX 77077, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.5705632, 29.7714443], "type": "Point"}, "properties": {"photos": [{"width": 3024, "height": 4032, "html_attributions": ["<a href=\"https://maps.google.com/maps/contrib/108143329814504597326/photos\">State from Jake farm</a>"], "photo_reference": "CoQBdwAAAK_2FWnBLDbthl6L-2LEVsmX7Wndie30n9F_V-ikkp7ro55ohrW6c7e7SV3A5P8av58i_riPGdW5UZ1FTClAqBRP9XA4vrr6B_JO7NJu-GOzdobUMJtNXhf0XawokfjlW9DVzCamDxwRj2dxEh_SdqWwBMKD7RPgoCFHNKRUNSwNEhAyFIJSbEwNdgxkgJ8ee0BFGhStsxYvztpaz1nrPdv5HgsZ_JiT2g"}], "types": ["park", "point_of_interest", "establishment"], "reference": "CmRSAAAAAwKH7BT1bV2QdKkNO-hV3HAOOe1Mr1_5C_1-yXPmWQ0X-FPRV5RwdeDdWjyJWgFXo0CTQjCl1DzU7HN9bSovd_AoSJZk0MWKrwZvcI8kzv206RzuwMtOwldGerOLmvpMEhCNhdMg3WixIIMycTXlyI5MGhRFbk1-7ff8FNbUUgjs7Uh3pGL0lw", "name": "Houston Audubon Society", "rating": 5, "id": "050a5458d86bdd1cee7b09678bd6256d0a20a73e", "job_title": "Yankee-Candle-Company", "place_id": "ChIJlQOxwVDbQIYR2uX_TZl0TYc", "address": "440 Wilchester Blvd, Houston, TX 77079, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.56820189999999, 29.770778], "type": "Point"}, "properties": {"photos": [{"width": 1800, "height": 1200, "html_attributions": ["<a href=\"https://maps.google.com/maps/contrib/108765250995932379967/photos\">Audubon Docent Guild</a>"], "photo_reference": "CoQBdwAAAKyP3BWoPYEZqEoy5nrF5liAxJyk02ArjZ9UPPHikITSaCGeNU7Ib-0UMn2y9J4kowVLmR33Lobif-um7NZAP3BgND5x1JrD6KIgXrzTjuFYtCSpV4HOu9J2Vz0uuoWpHrmJ5LvSgXUrtRJMe2_RArEYCKXaVdvB210ZvYiH0uC_EhAY19EPuRX-VZ9DuhkEXlVOGhTWPcag-S_0WmyXwKu2b2Ojz_Rrpw"}], "types": ["park", "point_of_interest", "establishment"], "reference": "CmRSAAAAdYkchDKxQqDZCzBBjBMpZEjWOAji_NhvpbrtKkY5h58V9PcSE-k0nEZPolObuQuKHdA2Je8vVdqKJMuz091ErAngq1_W09vt68ZXV_QeU7N5rlDie0gskIFuHTrGS4bsEhDIW-9oiuCAAQ0GP_ekrOY8GhRInxLnD78MI1p02yaSG9YnEYU56g", "name": "Audubon Docent Guild", "rating": 5, "id": "7ddd5daf76cc4979e2ba6b062322d1c77d5d1c07", "job_title": "Yankee-Candle-Company", "place_id": "ChIJI9XyNFHbQIYRtwHb8EtTpeU", "address": "440 Wilchester Blvd, Houston, TX 77079, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.44932349999999, 29.7803218], "type": "Point"}, "properties": {"photos": [], "types": ["point_of_interest", "establishment"], "reference": "CmRSAAAAqo5kbFlRUzMCsZVG5YYigJLO7tPRRHg8RrZctUFkRvFI0M-rg1-I61uauc8KuYkuYbrG_ebU0k-Gb1CvK9TGMwZr8GpdBjO3H74NR6cpMpLOYhVRyvV54ECOmv2sqdvjEhDrjx1TO1eygcx8vvHUHyGWGhSkflUIaOa6Tiksyu1iHrwSOgXaGQ", "name": "Coastal Conservation Association-Tx", "rating": 3, "id": "7258b034e119f31e82320bca6e72781ee9f79d75", "job_title": "Metropolitan-Transit-Authority-of-Houston%2C-Texas", "place_id": "ChIJcekacM_GQIYRPzL13cgQrPk", "address": "6919 Portwest Dr #100, Houston, TX 77024, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.47039, 29.655454], "type": "Point"}, "properties": {"photos": [{"width": 5312, "height": 2988, "html_attributions": ["<a href=\"https://maps.google.com/maps/contrib/101184977609161362375/photos\">aug4</a>"], "photo_reference": "CoQBdwAAAK7Tg4dOxbk8a9c1bsxha0hBSsaKWj-R2752Xq4-6WBbihsZYeleBRAiWslESA3DGD2Jdn1Oibnujc3ZWL2JjvZHTKaVS0m8v6XnTzYQXSqkM_5vVD3R9lHbJwBLH8Z3tBxYUyGZ42pTM1zvWZlKlseUdOCGI7YlhS9g5wtG0UYGEhA6ECgF8DTcksg8q96tAv6RGhTWgft9uCzPoCbKjR46NYcPVZY8UQ"}], "types": ["park", "point_of_interest", "establishment"], "reference": "CmRRAAAAJkpRpYKutcD_FzM6cSWi0uwIfyAcl_jSU8lWkmuOYuN5CPc191Jh5dMNPGccjfa9jaeZo1q2W0OXs9qQk_ua3Haf5JTdw3bY9tU2L724G-lnWFnaEZEg5UQG-mSxLyWwEhCPI245wu07s9-LOCh_aN4nGhS0lZn54lr6I_C2sbot7axYohRhjQ", "name": "Willow Waterhole Greenspace", "rating": 4.3, "id": "0127506e8071350c2d48f0ca56e939045297a0f4", "job_title": "Metropolitan-Transit-Authority-of-Houston%2C-Texas", "place_id": "ChIJR6_2zTzqQIYRsA7wExgfDWs", "address": "S Willow Dr, Houston, TX 77035, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.4003322, 29.7388505], "type": "Point"}, "properties": {"photos": [{"width": 1136, "height": 640, "html_attributions": ["<a href=\"https://maps.google.com/maps/contrib/117056878997299689379/photos\">Marisol Brown</a>"], "photo_reference": "CoQBdwAAAPUT2nIrVWnc3Lk4_p60_lq5EOjSfM0V0GNseUgNndez0kRidQfdGMcK__GlsDAzJHP1KyPJDAwF1mn8IX9Xvk2uD-jzPRIyNrV_GKmyXmDR8q9Z3SQ0eMEHL5Xaio2Ioi0RNG3x31AVMLe1kB3EiYBCcgObr8AUVdpGkNJJVoZREhCqxmfrWSZXqn6FO-bGdp_tGhSyW4h0Mk0jECe1Su1YKroyX6gLkA"}], "types": ["point_of_interest", "establishment"], "reference": "CmRRAAAAkoF-UkL3EIErW-EByluoHktFfDSad20nM4S6ajYXVlkl2xMsZWbunOVKarkDxCGRn9jn_-myBPX4zCcY7pHZIzU7lhEUZo7aIvwgOJDyXijbTrNhdYzy5zHl9HTqTjHUEhAb34Q3Sg_gFv9gStJMkdhlGhT4bsMf119M9L7ejaUFDaznODEsPQ", "name": "Masters Fine Art Conservation", "rating": 5, "id": "a462c2eef4e22ea319485ae7b84f3d20756cbdd1", "job_title": "Metropolitan-Transit-Authority-of-Houston%2C-Texas", "place_id": "ChIJp8u2bZvAQIYRbosnWz6cVmY", "address": "1612 W Alabama St, Houston, TX 77006, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.3876169, 29.794149], "type": "Point"}, "properties": {"photos": [], "types": ["art_gallery", "point_of_interest", "establishment"], "reference": "CmRRAAAApFE0670VCOQvl5rbW7uNUor2pykkyjG3ratfMauTtuTan3Ahw23nKjHpmjDS2wYL9iC9jm_XWmn15GIsC18N9UeNDXXSTxTF5qafR7Jz8uB-x6xn1wf2IC3xlhMTatHaEhCUcbJzfWrNOkQGP6Tkt8xWGhT4oky7qyXTDr7tkxMMhdPne4JM4A", "name": "Whitten & Proctor Fine Art Conservation", "rating": "NA", "id": "883a8c5ef35ab28e1630235ad65a6b16506a67fa", "job_title": "Metropolitan-Transit-Authority-of-Houston%2C-Texas", "place_id": "ChIJ8YuXE6K4QIYRn1SF1hazFEw", "address": "1236 Studewood St, Houston, TX 77008, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.3858767, 29.7300997], "type": "Point"}, "properties": {"photos": [], "types": ["point_of_interest", "establishment"], "reference": "CmRSAAAAswBCwCKRHWGVbQlqBhNyOeMAyN76RrZ8USh2Y6qqHAknJ382SuLyftkIP3VBBJe1T24_8qI1TzFd2p2TQQibMvgu_3bINV1wsbdromLkx5CosCnbCMfwP6H43bJVH6Q4EhA6oYttYP5FLmYWD0Kt5YeaGhTlHg-YNkXjUnA331upL5KgwhxvAg", "name": "St Mark Fine Arts Conservation", "rating": 5, "id": "ea2d4bac6d74716b33f456dff3aae0cc0b43cca3", "job_title": "Metropolitan-Transit-Authority-of-Houston%2C-Texas", "place_id": "ChIJKbDEoXm_QIYRcRFBlp0dE8A", "address": "4901 Main St, Houston, TX 77002, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.483218, 29.7482286], "type": "Point"}, "properties": {"photos": [], "types": ["point_of_interest", "establishment"], "reference": "CmRRAAAA-C1THorjzGC7i7ney2RwIyAFZO1lhiP3mRmR_pu0NkC-PNXeVZp_Ea93YbSgDmNqep4PQDRsSehwohVjf6RA8Qeyy634LPCwfmSnphPYfaiB0uJubkq8gn2vl6JsNfcUEhDUIVcDTyumRroMySgn2O7rGhRSdNEj_gkBHghq648Z0X7gx3hSRA", "name": "The Nature Conservancy", "rating": "NA", "id": "90af6fb9fb926dde9f7103577cebc4150bbb1dec", "job_title": "Metropolitan-Transit-Authority-of-Houston%2C-Texas", "place_id": "ChIJq-m4EX3AQIYRJkn4Lhccp2E", "address": "1800 Augusta Dr #240, Houston, TX 77057, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.42318089999999, 29.7345943], "type": "Point"}, "properties": {"photos": [{"width": 750, "height": 437, "html_attributions": ["<a href=\"https://maps.google.com/maps/contrib/106788706324997826205/photos\">Erika</a>"], "photo_reference": "CoQBdwAAAKQztmSWL_BWb1mx4lIPmh2tmJsDJJsuPpXBHyoNmrU65isBdOTaBsKSkMWxvuab_1E-_Ib7U1iykEhCHpVXoXbkksSgkumBokBf78rDIDJANWYRCpfEJKUMYUbUbgw_SvjcB136RlUPYOKyyDT0OICltdPy2Inq524rgNfMvvWxEhDUuSFvLkvuPloAkNUF6Rf7GhTp5jLT2drxzobeHCC6zlmr4pyYHg"}], "types": ["point_of_interest", "establishment"], "reference": "CmRRAAAA52aY_kM0Hf5ze_kRBy0qWphfA03BjTZf18Xp6aHMEYJYAF191gnXPYRe3pJMqsDNUN0NNHIzcic_3fSvZ15LSySfowk_4-GsF2I-wg4MlOp6uqKk5VE-UFqEqSwrMZcKEhBcxGQgGgmSizYQuqe_JDc7GhTcQrgkrD96QuO4-aQgSDgwuoi8Aw", "name": "Student Conservation Association", "rating": "NA", "id": "1c5ea7722fc0d99e9f7dfca55f5d9078224d51d3", "job_title": "Metropolitan-Transit-Authority-of-Houston%2C-Texas", "place_id": "ChIJQcqBXfDAQIYRErawO-goGj4", "address": "2990 Richmond Ave Suite #400, Houston, TX 77098, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-96.038102, 30.055621], "type": "Point"}, "properties": {"photos": [{"width": 984, "height": 985, "html_attributions": ["<a href=\"https://maps.google.com/maps/contrib/110279808588468038448/photos\">Peckerwood Garden Conservation Foundation</a>"], "photo_reference": "CoQBdwAAAGkPW1uwPyeajssw_0xsi9R5dd5gDtfDc7c0m8LEUL9BG6mjwrftiC0PLMZ5OffUjOmQCdVQJi62pFwJUdcfgSIYGS3fITEtOj0t3rrXgMLyRvhMqGsfQVTyav65jBPPMe_1V9wIecEDqKLdZ_vEaYIKz_vC4b8_3_vkrE3tnWUYEhCgJqCRVTuevP67GdwnEXCFGhSoWLjegHX6RPrSbUzgeVr1QlhsCw"}], "types": ["park", "point_of_interest", "establishment"], "reference": "CmRRAAAAD7MUH7KgOC5HjoalF-YPwjlMePRb3PhiLYwMy39pi6ABH1L5NxGqyYm1xGeFRj5vNxQx7JWFU6ok1AiNen4CwZVUjO1yhoB40zTVnvIv5mtr61FsHUWsqr-QYw6z9iFAEhDFrfX6f33nOyCkwDVSAQaAGhQP2XidULFu9G5hEle0S1NzO0gHfA", "name": "Peckerwood Garden Conservation Foundation", "rating": "NA", "id": "e618a4c618cd67ce4f5fdc165f640220ab3b53b2", "job_title": "Metropolitan-Transit-Authority-of-Houston%2C-Texas", "place_id": "ChIJmUR7pvHKRoYRIIl0o73bPGE", "address": "20559 Fm 359 Rd, Pine Island, TX 77445, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.64386449999999, 29.7515036], "type": "Point"}, "properties": {"photos": [], "types": ["point_of_interest", "establishment"], "reference": "CmRRAAAAJHba8LBPQwuYbTzHeY-1CzUtjdGOVGD-rX95yi57oXSEvGWgZZuBmv8gF3b4bbPe1sp82jOBNgLUCcxgPosxBwkrlGruy6koUec5AiOj80tRoFf6Td6BaInr2vmNZKIfEhAF3i1fvWPBk6TutKgSOd0-GhSZzVKtTeVQ6R7dsgvEX4e9DrJhZg", "name": "H2O Conservation Technology", "rating": "NA", "id": "30c07988ef8dfc62dac712b9d587daa4a36f2539", "job_title": "Metropolitan-Transit-Authority-of-Houston%2C-Texas", "place_id": "ChIJIWZRKeHKQIYRXxta3wOMGGc", "address": "1725 Hwy 6, Houston, TX 77077, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.5705632, 29.7714443], "type": "Point"}, "properties": {"photos": [{"width": 3024, "height": 4032, "html_attributions": ["<a href=\"https://maps.google.com/maps/contrib/108143329814504597326/photos\">State from Jake farm</a>"], "photo_reference": "CoQBdwAAALpOYlGeKT1HUeMnms67UxwEEYaJKMIKdmVB7fKEJBKMExPrdBVXX_jEMJix6Bg6940jIOCRnKz__iSdt4SvmvHLw6nQl_cjiPNsfXcKElUrVCZkJI_WLyFH3tE1uxT4DxmOIllSwWw98dGxeFTQMES7uJbDsy6l1fqHHlu9uk1HEhDmFXg6As3Ci43ZWoGInwwuGhTQwTkjccH7g2Li-tTs6GsJK3Su0g"}], "types": ["park", "point_of_interest", "establishment"], "reference": "CmRSAAAAk0O2y7N5EH5Ju41wOEaCDrirhzebxZQJ-tB4sM_uC7GKmUwZ2wEHFunhJFowonGhM3vQgfBP1WDVdHpgMauz9oRgxUGcWz49l4-hFMqUk9yZJVxSIT4cb9EFMTQ7bgKREhBYgLl7-ROYUWo3UOMkORinGhS89Itg_rbBQ2N1gtxGyeFuCWKGSQ", "name": "Houston Audubon Society", "rating": 5, "id": "050a5458d86bdd1cee7b09678bd6256d0a20a73e", "job_title": "Metropolitan-Transit-Authority-of-Houston%2C-Texas", "place_id": "ChIJlQOxwVDbQIYR2uX_TZl0TYc", "address": "440 Wilchester Blvd, Houston, TX 77079, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.56820189999999, 29.770778], "type": "Point"}, "properties": {"photos": [{"width": 1800, "height": 1200, "html_attributions": ["<a href=\"https://maps.google.com/maps/contrib/108765250995932379967/photos\">Audubon Docent Guild</a>"], "photo_reference": "CoQBdwAAAJ2iO9zwzBLA8-_BCRRdYZYGA765DoCbnC4IrDkhic4x-P6OI7JzM30DDwySM1LRZ4s08s_-34FS2gy0ZR15o0UUskI8BhwdONP0D-v2QbWKNWkzzaML0MpqePJN1h9LgDdmjCyOPnDDaWzGvSfAxGwao9Fbqf47B-GcTE5ejC8AEhCOWPflarw9l6DWr_ZrhxdEGhRakTLQXND7vCE1ODJIM5x3GZj1Qg"}], "types": ["park", "point_of_interest", "establishment"], "reference": "CmRSAAAApucbQhdv859XCXkmDXzJ70MHOX09XcCgo-MOfwTyKkBk5RqMdQUmstQ1SJd94qjCDqpj_2CgkoatZzkC05MXS9nLinrbta_zcmCZvR-j8h5tFNsRKDEdXa0xtHH2w2zIEhDDKPO1ASNvgqkNUS32y3PNGhT_7WoToDilqS-tIRiNdMoPh37_Bg", "name": "Audubon Docent Guild", "rating": 5, "id": "7ddd5daf76cc4979e2ba6b062322d1c77d5d1c07", "job_title": "Metropolitan-Transit-Authority-of-Houston%2C-Texas", "place_id": "ChIJI9XyNFHbQIYRtwHb8EtTpeU", "address": "440 Wilchester Blvd, Houston, TX 77079, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.44932349999999, 29.7803218], "type": "Point"}, "properties": {"photos": [], "types": ["point_of_interest", "establishment"], "reference": "CmRSAAAAeMuVNtwH58uFd3r9URn4JHU1tWCR5G8TbhC_lR3HGlOy8umY6NXJZSV9313ae-p8f3KtG26kgASZSBFYDRcvtWU7meBRsluAWRshNLbDAEFtLBrComErYoep1rM6f8suEhBTfjNHM7uevqJSoeaHXnRFGhTXMy7vsogYyiGvgG2sOJrN-ELmiQ", "name": "Coastal Conservation Association-Tx", "rating": 3, "id": "7258b034e119f31e82320bca6e72781ee9f79d75", "job_title": "Property-Damage-Restoration-Services", "place_id": "ChIJcekacM_GQIYRPzL13cgQrPk", "address": "6919 Portwest Dr #100, Houston, TX 77024, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.47039, 29.655454], "type": "Point"}, "properties": {"photos": [{"width": 5312, "height": 2988, "html_attributions": ["<a href=\"https://maps.google.com/maps/contrib/101184977609161362375/photos\">aug4</a>"], "photo_reference": "CoQBdwAAAC37IEozvteY2A6oslah5dJsjBDJwdhFmZuVGSqpumpv8SEpH2D6QBZ77RXOY3yT1fXiEhq36hdyDZ1RrgKgVFHEbxIQaBmIOtV7S2vRMGBUUtZgKAIj4aOK21RkS7d6mbJmNIdPPsLZcPXu4Jt03kdikewLgFHHj_hC8I_uJH3UEhBbRINchr8ijITXAIM7-XqcGhTS10BZxdT-c_IZ6ESoUBLMme1aEw"}], "types": ["park", "point_of_interest", "establishment"], "reference": "CmRRAAAALqy1C8j2T3EoUAfzdfCOcFEDWBlMXELkARw7yGgbIH-Qdu4IftburVrcG7bKDTq5bs8TuBEbbmMP2vaU7Eh8fVOeay7dQYoYH3Np9rDmmLU0U3vHs-fhPqb0P1awvyzNEhBs-80TJgKTKrkRQDi-MPVaGhTieYNBxVstkJgR3_T1hoG5PDAAYg", "name": "Willow Waterhole Greenspace", "rating": 4.3, "id": "0127506e8071350c2d48f0ca56e939045297a0f4", "job_title": "Property-Damage-Restoration-Services", "place_id": "ChIJR6_2zTzqQIYRsA7wExgfDWs", "address": "S Willow Dr, Houston, TX 77035, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.4003322, 29.7388505], "type": "Point"}, "properties": {"photos": [{"width": 1136, "height": 640, "html_attributions": ["<a href=\"https://maps.google.com/maps/contrib/117056878997299689379/photos\">Marisol Brown</a>"], "photo_reference": "CoQBdwAAAMqgJGWS4qBLZbfw0sXjEoPpFKt2kwSmu0iWt1DNNiLc-3MFcLT9DPfV7HADUn6Hdf6ahj6cyb5SX69swkHRyegf1xnGZ2JbybLYBttmd7rvU1CH0CWX6Pj9aQLF9bqhuRKPwWiKC3kQzGNUJIHilxPUdxmDk0SraZcxzf9M9GoNEhCgbHHkWdL4WDCi0CVEFjHpGhRHuOcy3BgWwpGFJVXFnuHtztqIYg"}], "types": ["point_of_interest", "establishment"], "reference": "CmRRAAAArpwr4S0kFJ5Df_zNf5Z31XnHGacJZhM4pmDWCq8yvccH2lkn-vlssMcvil-MpVUSOAzD6BFfOA1GHTSpaKtJDNDLQJDV-wSP8ZVKWOeR5MQCx4hh0SkQWFrqO7CfzkYrEhAmlVnk8jViZJsJa--GoqI5GhSnHqAcvnkjsc0WkQ5KdhI6IZrIbg", "name": "Masters Fine Art Conservation", "rating": 5, "id": "a462c2eef4e22ea319485ae7b84f3d20756cbdd1", "job_title": "Property-Damage-Restoration-Services", "place_id": "ChIJp8u2bZvAQIYRbosnWz6cVmY", "address": "1612 W Alabama St, Houston, TX 77006, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.3876169, 29.794149], "type": "Point"}, "properties": {"photos": [], "types": ["art_gallery", "point_of_interest", "establishment"], "reference": "CmRRAAAAr65M_x51OuGSCt6ZKXuhu5I9cknyOdTiZqCAuqN300Nm8g7ukFoQYJxoljqzY3jAZ6-7aNMtyhX0H0iLq4HYuGDmc9RDLlY2mIkUvVwNKCtAMcnLKy7qhfeyIObC84kYEhBwQZnkspX66NcNuFVmjwR1GhTlDAV3p5KQW-NXYDlE0S_TitcsMQ", "name": "Whitten & Proctor Fine Art Conservation", "rating": "NA", "id": "883a8c5ef35ab28e1630235ad65a6b16506a67fa", "job_title": "Property-Damage-Restoration-Services", "place_id": "ChIJ8YuXE6K4QIYRn1SF1hazFEw", "address": "1236 Studewood St, Houston, TX 77008, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.3858767, 29.7300997], "type": "Point"}, "properties": {"photos": [], "types": ["point_of_interest", "establishment"], "reference": "CmRSAAAA_zgIRNBz5rc9bjyieYYOw9rVBFyNqUyFTYnxJ6-mHjeStf8YUTpcCjInDcnPWgIjSBlXbPm1FOTqBVfyB5sBga2Nk2v93UDBKyI3vW5gmFTj0_1rvt04V7vWGR7X0kocEhAwStGZZXJoUYqI3czVe9jxGhRItpQMgGqgaDGH354hT-E9VJQWqQ", "name": "St Mark Fine Arts Conservation", "rating": 5, "id": "ea2d4bac6d74716b33f456dff3aae0cc0b43cca3", "job_title": "Property-Damage-Restoration-Services", "place_id": "ChIJKbDEoXm_QIYRcRFBlp0dE8A", "address": "4901 Main St, Houston, TX 77002, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.483218, 29.7482286], "type": "Point"}, "properties": {"photos": [], "types": ["point_of_interest", "establishment"], "reference": "CmRRAAAAy82piIetr1epJ2NXW9hIpdARX_cB5g5Ke1AZSHzDaeHs1BoavTHu0Hr0r7cSbyPtYxPNAf2Je951SvakCpEndud9LeOsXsRZ213mh2qzSKcAFvQN11-M2fDgHXc6RgaxEhDrE3599zhk4M49Cb1YOZzkGhT3pIDDAagrnoRaDdhtcgxlNaEuMg", "name": "The Nature Conservancy", "rating": "NA", "id": "90af6fb9fb926dde9f7103577cebc4150bbb1dec", "job_title": "Property-Damage-Restoration-Services", "place_id": "ChIJq-m4EX3AQIYRJkn4Lhccp2E", "address": "1800 Augusta Dr #240, Houston, TX 77057, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.42318089999999, 29.7345943], "type": "Point"}, "properties": {"photos": [{"width": 750, "height": 437, "html_attributions": ["<a href=\"https://maps.google.com/maps/contrib/106788706324997826205/photos\">Erika</a>"], "photo_reference": "CoQBdwAAAPcRS_r87fr-ztbXjsWuBXF4E7o8DD6gYk8ABB3hdHftCL9ykqq5Avt13h4PmdQBlkn62tkJ_8AVS6qKHDjIW5K-uJzEh7xJwSICRFxffNX3VImkGcSCSBFSWc7s0j7OCLyabRlQcJwaJ-Y2i4W6uXfO6luEYKL7A0mbsJK2JkiAEhCd8l2brzNzQeQXsM_97QjaGhQlun7laTcc8YTSU74pIs0l07UKpA"}], "types": ["point_of_interest", "establishment"], "reference": "CmRRAAAAfF6lompf2-9WIGm6YguIfyMKBCHpF0_43qYVXqynqLbvNXWY5PGhp28Y8PdRLRmCCDA9FACXoxQ4Ngetu26GXWnKIB8ISj8nSNCYYj1mAxyai2tQ1q9VmldpMalEYIzcEhCDjD3j7bHtdXmFHbft1a7UGhR25KGUYmnxpin9vE9RIlnPVuMWRw", "name": "Student Conservation Association", "rating": "NA", "id": "1c5ea7722fc0d99e9f7dfca55f5d9078224d51d3", "job_title": "Property-Damage-Restoration-Services", "place_id": "ChIJQcqBXfDAQIYRErawO-goGj4", "address": "2990 Richmond Ave Suite #400, Houston, TX 77098, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-96.038102, 30.055621], "type": "Point"}, "properties": {"photos": [{"width": 984, "height": 985, "html_attributions": ["<a href=\"https://maps.google.com/maps/contrib/110279808588468038448/photos\">Peckerwood Garden Conservation Foundation</a>"], "photo_reference": "CoQBdwAAAJA4wnZnB9Fz4Z8r-P2TXTpZWR0WPdvYloy1WWEC4FO0aUwL-Gm8Soi7IV-l8Y4SOpyq531uRVnT4L6nOzKkC4VsPD0odLT1cHCBkMIGlXdfZxwRobL9zCTEHZe6m_zEZpU52cNy_DTDwk5XdC32ZLz6ByVTGTk9fZpzDpjODVgoEhARzh6LvY_6GEDefiy56ZEdGhQILqayvHTOf37CBLXrP6oW1sPzUg"}], "types": ["park", "point_of_interest", "establishment"], "reference": "CmRRAAAADgqxPJNEpB9GSjhY1gntfv-NtFdzfZxMYS3Ab5ysT9nF8kVDgJautFsEZylCivlTC6youU_HzMjnorozW0y_lLDzKHRRp5eiUTLXK-FHI32_XFc72wb8sHJD0OJAOfDMEhB-TVbXmG7Kn8dxZFaZOHUvGhQfn0x_TAdktpdgGL8WTVDmjo08BQ", "name": "Peckerwood Garden Conservation Foundation", "rating": "NA", "id": "e618a4c618cd67ce4f5fdc165f640220ab3b53b2", "job_title": "Property-Damage-Restoration-Services", "place_id": "ChIJmUR7pvHKRoYRIIl0o73bPGE", "address": "20559 Fm 359 Rd, Pine Island, TX 77445, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.64386449999999, 29.7515036], "type": "Point"}, "properties": {"photos": [], "types": ["point_of_interest", "establishment"], "reference": "CmRRAAAAf2ff1yCx9Ok77WEa8W9NmM8G8T6qjruOGqHD_MKExqK7ObVpNNnkYU_spAX-Bg6Bp4YE0OzZV7t839fOZH3ORbQneso-8XQV8IH2sNZ3ejh5_Oynqj5v45K_Y3DkCaAAEhDlie8qNj-YCMGpLPv7hlGlGhRs4OmlHZs_c_zjQyChIgaESqpBSA", "name": "H2O Conservation Technology", "rating": "NA", "id": "30c07988ef8dfc62dac712b9d587daa4a36f2539", "job_title": "Property-Damage-Restoration-Services", "place_id": "ChIJIWZRKeHKQIYRXxta3wOMGGc", "address": "1725 Hwy 6, Houston, TX 77077, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.5705632, 29.7714443], "type": "Point"}, "properties": {"photos": [{"width": 3024, "height": 4032, "html_attributions": ["<a href=\"https://maps.google.com/maps/contrib/108143329814504597326/photos\">State from Jake farm</a>"], "photo_reference": "CoQBdwAAAA13aEo_8nijNoJKkob0A1inXB46TqMOJsYlId5gK_yZp7mUGHZ5LCMeFx2BEhzLE08oeMAugAoTyL_6JQoT8I31C2_23vT6wHj7qjVMvwG5-O-ZF7pIkM2FwRF8-IrEj63L7bUnLZHr-_J2ugfkhCHrChJkj8iw32LAq2SIKlEmEhCerMQcyp3bS5d64lfKlUwmGhT5F_7UJ4W6riS38UWwML5tGquEog"}], "types": ["park", "point_of_interest", "establishment"], "reference": "CmRSAAAAtyUlj9OPRl8pIVYE55RmgjoiNKwPs0sjvXiMRL8-RHYfqd46ozB35zq5fozpCQHVEVJJb2Fvu-4PvFIIIc8hA5htNwyOy7NFMfjFRDHLid3m6PYxNqwVaCVJE4ZzF0fXEhA66RPFRvnJtOgEGYsOeN3yGhQxf3OXxp4Xe277V2Dr3PZ1U4Jmtg", "name": "Houston Audubon Society", "rating": 5, "id": "050a5458d86bdd1cee7b09678bd6256d0a20a73e", "job_title": "Property-Damage-Restoration-Services", "place_id": "ChIJlQOxwVDbQIYR2uX_TZl0TYc", "address": "440 Wilchester Blvd, Houston, TX 77079, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.56820189999999, 29.770778], "type": "Point"}, "properties": {"photos": [{"width": 1800, "height": 1200, "html_attributions": ["<a href=\"https://maps.google.com/maps/contrib/108765250995932379967/photos\">Audubon Docent Guild</a>"], "photo_reference": "CoQBdwAAALxsJdjI1LnudCTbg0MZPquEK91o_zVjfFN34V9XZQoKKXjnVUyZiu8CuZ0ID6dDot33f27aibK1spAwb5r0nUO3Lu0pFfwlUJU5JFDNGSXhMN15uC99g3QTg_KrekLQSHGItuRSW1ccW6AJb5M8kPMAf7Bd1BNhgj0h2jN3qQA0EhBBAYmDh3gvvkf_ynSDdZwVGhTCeemYBDOprcmNt68bsn0VZmI8Kg"}], "types": ["park", "point_of_interest", "establishment"], "reference": "CmRSAAAAxEnjhSMykHi30tM3J-8QibydJPsmxxWoWG55qzwdHNwBL42Pt7K4uCWBA8dn0v7jFzV-O_uoP0OOpWnsTjScUZ9443yt-XdXXtcGPJHeDa1kqm0Hd6RMeO8Co1Bx3uQdEhDUe8U8oN0orzQj5pQhnv7sGhScUMwie8lp0g-Vtxte3cfW_Ss5rw", "name": "Audubon Docent Guild", "rating": 5, "id": "7ddd5daf76cc4979e2ba6b062322d1c77d5d1c07", "job_title": "Property-Damage-Restoration-Services", "place_id": "ChIJI9XyNFHbQIYRtwHb8EtTpeU", "address": "440 Wilchester Blvd, Houston, TX 77079, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.44932349999999, 29.7803218], "type": "Point"}, "properties": {"photos": [], "types": ["point_of_interest", "establishment"], "reference": "CmRSAAAA75qt2h9zsMoNG8d37xJ_wnnIOeZX_HhGEhSyTypVCijz7_MVi6armqvsDsPX710IZYtzzt0V2Q_84TAVAALTnJ_xQV05LVwbHmNJJ4AZf9nHkwySxM6RmjwVsD9F3RjrEhAca_cnkvJ3ZyIPxXyXYup6GhRZgEW5K9xcLDc2cxBGq5VSkzAnGQ", "name": "Coastal Conservation Association-Tx", "rating": 3, "id": "7258b034e119f31e82320bca6e72781ee9f79d75", "job_title": "Univar", "place_id": "ChIJcekacM_GQIYRPzL13cgQrPk", "address": "6919 Portwest Dr #100, Houston, TX 77024, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.47039, 29.655454], "type": "Point"}, "properties": {"photos": [{"width": 5312, "height": 2988, "html_attributions": ["<a href=\"https://maps.google.com/maps/contrib/101184977609161362375/photos\">aug4</a>"], "photo_reference": "CoQBdwAAAGIKTp_9Q8zIF3TCjazvumEj7HRDfyYqRVxxcJeHIj5X6Xae3KvgKzzAHEgwPrBYlk456M-MpzAtndbR1BSSjiZtF6Er9dpPX8O_RP6D9NHnUJluw6IjYNu0N0JUXvQTGMHyGagOaAUHHiNhOUFqCOZY5RXAapZtAo_1DBCNU93nEhB5xY6OJ_6OpZOsSgB3E88zGhTqCRa38WBD56lsVuDmieL2EsD4NA"}], "types": ["park", "point_of_interest", "establishment"], "reference": "CmRRAAAAP8XKahbMW73rY38TvvMunMKezy7gtBsR2GF1Y8IzBo--fRI30AG5FVDEvohKgnNnxZtjAvy15twAoDVEMHt_xhAqO_m_hrmENUmIZCzeLl0xJiWVM66upo2_bASOIXG8EhAZKC8e7SQZZlcEefg70nVHGhTYmd-jCZk2TH23wGmXbFKWAv7h_g", "name": "Willow Waterhole Greenspace", "rating": 4.3, "id": "0127506e8071350c2d48f0ca56e939045297a0f4", "job_title": "Univar", "place_id": "ChIJR6_2zTzqQIYRsA7wExgfDWs", "address": "S Willow Dr, Houston, TX 77035, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.4003322, 29.7388505], "type": "Point"}, "properties": {"photos": [{"width": 1136, "height": 640, "html_attributions": ["<a href=\"https://maps.google.com/maps/contrib/117056878997299689379/photos\">Marisol Brown</a>"], "photo_reference": "CoQBdwAAAPahnL1ndlU2p7oYvpIJaJY7EINf2-E9OKjAojWwsTI94mB2lm678EstjfCHg11y4lqpxWivMkR2wYaWrdlpzqhT7vP22za4ZNkKYJ9SO-H6zigrFFqRRJ4ch3r54cDsqA9vJ6ZmW-Bkcd-sCxM4Suq4TwjUJ-XrsD9SSbYxaSGqEhADebjVIuTMNoDFlGLAtUbVGhTmUgtmLkzcMqlnv-mDzqJboUHByg"}], "types": ["point_of_interest", "establishment"], "reference": "CmRRAAAAajADpfUzvIFy0r-NDdaduxXZbeQqDUuZ7GjsKggh6Td6Q7vXj5z8rfuFrOgzURY2fOy7HpmMrVm_tQ9JZCgts1xRlEQjMoWpPPQGhX-axMk24hSbGep9ESTklZiT0-DIEhCclR-d3JiiRr8oKngvUTYzGhQTjM8ISruZSivnNQHIFTQSe9Dejw", "name": "Masters Fine Art Conservation", "rating": 5, "id": "a462c2eef4e22ea319485ae7b84f3d20756cbdd1", "job_title": "Univar", "place_id": "ChIJp8u2bZvAQIYRbosnWz6cVmY", "address": "1612 W Alabama St, Houston, TX 77006, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.3876169, 29.794149], "type": "Point"}, "properties": {"photos": [], "types": ["art_gallery", "point_of_interest", "establishment"], "reference": "CmRRAAAAj6GT1S2KoXMf9HSuJuOMkPr4-U3U2mSfU0SUSQRtYIwXuFBsck1TYm2JdlqlW1BC-vW4advr4EmSFWjQdkhgLqR2BdRRIaiI7uMJrcBTgfRP0GWlGT4767V877uhn-01EhAXi-ODS8zAhw8YGXNaMwWZGhRs4_wlrjnXqUQZ1YnThqgjRgLZCg", "name": "Whitten & Proctor Fine Art Conservation", "rating": "NA", "id": "883a8c5ef35ab28e1630235ad65a6b16506a67fa", "job_title": "Univar", "place_id": "ChIJ8YuXE6K4QIYRn1SF1hazFEw", "address": "1236 Studewood St, Houston, TX 77008, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.3858767, 29.7300997], "type": "Point"}, "properties": {"photos": [], "types": ["point_of_interest", "establishment"], "reference": "CmRSAAAAJir4vlWkN2HiwJpSMhPH1K9KEsyDW1LObeJO3NmcPt1fvDFZfF1s9CDcekskBTsCz3_F6r1BY9D6BdJap51G8roJeKohWGWc0cQ7aAFj_zOhtVNqJTYmLRToQIaY0v1DEhAwcDQaYLRxxdFrWKlEAfAxGhSd41MFXOwhrsn3uanAe5Yb9-MfdQ", "name": "St Mark Fine Arts Conservation", "rating": 5, "id": "ea2d4bac6d74716b33f456dff3aae0cc0b43cca3", "job_title": "Univar", "place_id": "ChIJKbDEoXm_QIYRcRFBlp0dE8A", "address": "4901 Main St, Houston, TX 77002, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.483218, 29.7482286], "type": "Point"}, "properties": {"photos": [], "types": ["point_of_interest", "establishment"], "reference": "CmRRAAAAxdcitcPdyNB4eiC0YWu7OeVNjcuLY9ZUmW-4cAKjVpV4VpLQwFLP4slYCYzxE5cLYjHGaRwB36d614Xxichayqo0WFa0fYCsJKPVs1XcGK-xvspgaNYKgV2p2tWNu1_qEhCTwYAI-dVNpaer5tjfq_o3GhRU0AXpsQKmsAqZjt_udZ4nSIKfxw", "name": "The Nature Conservancy", "rating": "NA", "id": "90af6fb9fb926dde9f7103577cebc4150bbb1dec", "job_title": "Univar", "place_id": "ChIJq-m4EX3AQIYRJkn4Lhccp2E", "address": "1800 Augusta Dr #240, Houston, TX 77057, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.42318089999999, 29.7345943], "type": "Point"}, "properties": {"photos": [{"width": 750, "height": 437, "html_attributions": ["<a href=\"https://maps.google.com/maps/contrib/106788706324997826205/photos\">Erika</a>"], "photo_reference": "CoQBdwAAABAA8I9sygqGHJdw8S86jCsteps3SA_OYzLWC0qiaxFb31g-IlEEQiHbIyNAtjzNJkQp6kweuGe464BWS2iCnrVCPV4tF7f8LGgk6QRjlEOExzXC8hVRBW4wM4YA7_FPZAQ-7XTFBhGtB1PV811_PTEHYR73YvAzSJmF7LHdmbAcEhAinJJsK3FzNMAu2RRD693UGhR2q7778Q5FC_ZQ5iYncak0grYX8g"}], "types": ["point_of_interest", "establishment"], "reference": "CmRRAAAAwQE2rwFp9n_mh5B9T19Td9LulakDNNc16eWENkfvJzyF949IbsAf7E4712Tm5f1MNfQWEjwKrxIeXDM0m0Ebu6w-TUagsQTiHcZ9g2r0fR7HwO9jhIgDbBfx_jc317cJEhBlUMF97-qk2iSX3_N1ThsXGhSf2iDLSZzXDa3WisTq4rRk87paRA", "name": "Student Conservation Association", "rating": "NA", "id": "1c5ea7722fc0d99e9f7dfca55f5d9078224d51d3", "job_title": "Univar", "place_id": "ChIJQcqBXfDAQIYRErawO-goGj4", "address": "2990 Richmond Ave Suite #400, Houston, TX 77098, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-96.038102, 30.055621], "type": "Point"}, "properties": {"photos": [{"width": 984, "height": 985, "html_attributions": ["<a href=\"https://maps.google.com/maps/contrib/110279808588468038448/photos\">Peckerwood Garden Conservation Foundation</a>"], "photo_reference": "CoQBdwAAAFLl-E4drBhrEjTVp64rOJf1zKwQ6Eb9PZXQDQBjce_E0zcqPzyX8qELnoZwzJL2P2sMwEyrckl2K477Rph2POkb6PCg8q1n-uxK3Lj1jqCZI5-fJEytvf061Skq1hVL8FE6tXLfPuFrl3jSW_LLN3LEPCQO7mO7qQsrdhtveewzEhCKTBGG567CQLTybVm9Yg9WGhSLgsobzcRaZ1pKwTLP3SXX6tIuoQ"}], "types": ["park", "point_of_interest", "establishment"], "reference": "CmRRAAAAY1CIsyRFwbB1C80USFYTQcW56KaOzsQ_rEjIk2KMGtEoc4NIb5UWoadGkgkUGACtD7K4ZhTJcITPMdVqarzKtskcROaxj4gIhvKHtmhZ9xtaSPCE9swLpSfEHFeAcs4sEhDu1-c-JKszkj3F3Hu5fm_8GhScbZjJ_Mi7qIPMuMkgIadc7tmeHA", "name": "Peckerwood Garden Conservation Foundation", "rating": "NA", "id": "e618a4c618cd67ce4f5fdc165f640220ab3b53b2", "job_title": "Univar", "place_id": "ChIJmUR7pvHKRoYRIIl0o73bPGE", "address": "20559 Fm 359 Rd, Pine Island, TX 77445, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.64386449999999, 29.7515036], "type": "Point"}, "properties": {"photos": [], "types": ["point_of_interest", "establishment"], "reference": "CmRRAAAA7MIEBZET5wsVER7psQ_Z9IfFBiwJYvE5MW86PAkqZVNB9XPLgoVDqKH6-VW8uDntKwZYt88JcigjgPZ9XfRSYkmV3WPtkDTLusH--1nXo1C6TLjVrp0vxUikh223ipcqEhAHPHkQyLv-qDuKAfVTJAqXGhTdjNQE4oR5Vk40SPfpMolTTcY5Aw", "name": "H2O Conservation Technology", "rating": "NA", "id": "30c07988ef8dfc62dac712b9d587daa4a36f2539", "job_title": "Univar", "place_id": "ChIJIWZRKeHKQIYRXxta3wOMGGc", "address": "1725 Hwy 6, Houston, TX 77077, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.5705632, 29.7714443], "type": "Point"}, "properties": {"photos": [{"width": 3024, "height": 4032, "html_attributions": ["<a href=\"https://maps.google.com/maps/contrib/108143329814504597326/photos\">State from Jake farm</a>"], "photo_reference": "CoQBdwAAAJ2XKQNVo4YKrz6WB2dXYl-nxry96yezSvFOOElOLXyCOEiiBVf6p-EQY5PFMHXY3YhO3rDA8euHe2QCLUDk-GwaYZ4xO8ZKCeuPEDVbtXYBMvv87YIwv01prXzZCQtvFTnk6FaZNETHFFbn6WqHSLkIpEYNW8J9__23ZOMXVr_6EhCtWvGZGxqQEcxfaOELQ_86GhSIECaw2xEXSvaVpt3L4KJIVamaxQ"}], "types": ["park", "point_of_interest", "establishment"], "reference": "CmRSAAAAp8uJPS3N8bBuFcQofR9vwwlIzUDQwZvuSbOUDzjsJAawV3ZOIt4mQgUIgPtSScXjFiczbj5albo3NuGmV7OrKCs7W2ln3xXNQ7byNfbjGVM8LhcJ1HU7PPpsTx178etMEhAMa7NTveQHIazAFKn4iQEpGhTCZ3i7_q6bV1NoEoFjzFWEuCRhCg", "name": "Houston Audubon Society", "rating": 5, "id": "050a5458d86bdd1cee7b09678bd6256d0a20a73e", "job_title": "Univar", "place_id": "ChIJlQOxwVDbQIYR2uX_TZl0TYc", "address": "440 Wilchester Blvd, Houston, TX 77079, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.56820189999999, 29.770778], "type": "Point"}, "properties": {"photos": [{"width": 1800, "height": 1200, "html_attributions": ["<a href=\"https://maps.google.com/maps/contrib/108765250995932379967/photos\">Audubon Docent Guild</a>"], "photo_reference": "CoQBdwAAAEbo4iK5u6daGIP8X4XCmAiJHYx6pS7WwXu0y1YzAPuJZHOXrtuG8lpbhy8TEEUxiRz9upOAf_4pmfWOrsVMbsOFlkT_4Pz2Ej36e580E3MaV-rxF06hr0QyXN92vxQYugQBYEDoIsmu2Qnij7QF3qB0yJf5JtnTyao0UxqNELViEhBfQ6UuFZYD5H_ZdjaAibW7GhTPp-BdutnJW4v7rq9Oz53uWC8dlA"}], "types": ["park", "point_of_interest", "establishment"], "reference": "CmRSAAAAjqgO4C2DDGx1sLMw0ICDhsAfmc1dtlbsGkzxHO4Px9PGh048wuJlmyvh6J2R1NV8v9n0yq9V96Dnl9P56E5GVCHFvx3qiNIuYdNMLQZxtdUuTGukSAa4GvQFfON_QNKeEhBJQ4PAXZcOqB7uDDdzfgIxGhSUpMlXNtqB8g3PKlaq05t3qXuutg", "name": "Audubon Docent Guild", "rating": 5, "id": "7ddd5daf76cc4979e2ba6b062322d1c77d5d1c07", "job_title": "Univar", "place_id": "ChIJI9XyNFHbQIYRtwHb8EtTpeU", "address": "440 Wilchester Blvd, Houston, TX 77079, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.44932349999999, 29.7803218], "type": "Point"}, "properties": {"photos": [], "types": ["point_of_interest", "establishment"], "reference": "CmRSAAAA5d3DzQiOswRXugQ6SN5K0U-3PkxjfYQBOxBJsb-5G2xjpK_p575c9nk3JkEEYJGihUSLPo62ZeMdoGnEWFwhFkjZUDB4RlO10M1EFozkDn5yAU4vfbaijcRq4VE7cMxNEhBrpLQqbQaPz0GuVbenzCR9GhSeDiAskwDnT8ll5TiGNJFYQ560kg", "name": "Coastal Conservation Association-Tx", "rating": 3, "id": "7258b034e119f31e82320bca6e72781ee9f79d75", "job_title": "Precision-Executive-Search", "place_id": "ChIJcekacM_GQIYRPzL13cgQrPk", "address": "6919 Portwest Dr #100, Houston, TX 77024, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.47039, 29.655454], "type": "Point"}, "properties": {"photos": [{"width": 5312, "height": 2988, "html_attributions": ["<a href=\"https://maps.google.com/maps/contrib/101184977609161362375/photos\">aug4</a>"], "photo_reference": "CoQBdwAAAPousA6PsWpu2NI72JhoJKtsizn4p1uMIUNX6IzLX7rttdJ20LcoV20WzzZy2eRuneitp8zxg_drAcU2oerxizCaVvh7MhMBUk6fpBUdzZXcNEbm9IiUzX6K7S-LXyrmanAKSEEAxnhW9ssTg0rsPJCjKT4E4nbfNwrJxfdtB9HBEhCI-_W41Bu0qMek3dNikuLbGhRtCjaDqqkoFJqCL3YBoPX727PMpQ"}], "types": ["park", "point_of_interest", "establishment"], "reference": "CmRRAAAAszGmrVJitTWAz8TPEMdpGIWEfi5xM-Bf_jWfnZcTn6lb6XDhmehPX-LvVbaU2Z6I06y-zhPF1swOJWo0SzfjCWdZp72izAslqQGOWk66uUD3Z20lYNABrxO3mS0EmC5wEhBVpJwCLz6E_7TqWI5fOk5uGhS1XbUKW0rKEfSQLuPXTu7kD6-G4Q", "name": "Willow Waterhole Greenspace", "rating": 4.3, "id": "0127506e8071350c2d48f0ca56e939045297a0f4", "job_title": "Precision-Executive-Search", "place_id": "ChIJR6_2zTzqQIYRsA7wExgfDWs", "address": "S Willow Dr, Houston, TX 77035, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.4003322, 29.7388505], "type": "Point"}, "properties": {"photos": [{"width": 1136, "height": 640, "html_attributions": ["<a href=\"https://maps.google.com/maps/contrib/117056878997299689379/photos\">Marisol Brown</a>"], "photo_reference": "CoQBdwAAAIZQY6YWDoFhy2M69B17Ux5xEAyqjfv2CVbiHcpIw9l8kxP8tAuRlqv02JRfVUMAbELFCFYxb88kM1BCRwoPoJVnzFhOG3vdEZyxmkijLZK3ikc8AZGq_nJWyBjCQqnhEdMRQ5PXlQiHLuwHtVla-XsE8ROg_zfRSMVVUbXaXRXSEhC0OwYATuIldc6EKVC4mO01GhQTR5R6Zfd9x-b9e19jbaFArFaJHw"}], "types": ["point_of_interest", "establishment"], "reference": "CmRRAAAAiSgzsqKB-TmvTYgwW8PVIXoZr8C4OTu7yz634ORpXtozLRacrc5Xp8rzbq_mXUcmRy5lxTrLPxgyK1INC8HZ35WYYG1Xh-NZv7xuRp08f8jIJgBaVic1bmJYl8Cupcy2EhDHu7yGXlun5U7FmBTRAqrIGhSMBqCIu8fglY_kD7QTSkbHkrDYEw", "name": "Masters Fine Art Conservation", "rating": 5, "id": "a462c2eef4e22ea319485ae7b84f3d20756cbdd1", "job_title": "Precision-Executive-Search", "place_id": "ChIJp8u2bZvAQIYRbosnWz6cVmY", "address": "1612 W Alabama St, Houston, TX 77006, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.3876169, 29.794149], "type": "Point"}, "properties": {"photos": [], "types": ["art_gallery", "point_of_interest", "establishment"], "reference": "CmRRAAAAlePzg4iBDZXyV_6tjhjB4nJo1sEl9V5oAVsAgScnYWNjGer7Fb7nBO0xJU6i3f3tCr7yZ03H0OL5hLWx3LUYLir4FoopLL9929cqHJse1yOourvzQEZO1kSe4ZPR16BdEhAGBoiP__UGFssJ6M-WDC44GhQIC_uGjg26IiW5ja-S9JorWZiTWg", "name": "Whitten & Proctor Fine Art Conservation", "rating": "NA", "id": "883a8c5ef35ab28e1630235ad65a6b16506a67fa", "job_title": "Precision-Executive-Search", "place_id": "ChIJ8YuXE6K4QIYRn1SF1hazFEw", "address": "1236 Studewood St, Houston, TX 77008, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.3858767, 29.7300997], "type": "Point"}, "properties": {"photos": [], "types": ["point_of_interest", "establishment"], "reference": "CmRSAAAAzJi9pJmC7KocYNUvQDnxn96gw5GmuLFwTBkzUog-kWVVAvKZ1Jr2CvZH-wfC8-3rz1bCJ3qKqmReyX3Mnf26ZjMQ5e7hUCH2I6tZV-nr5y9QM56oTQb3gatfB0nL0YrVEhC7hE2cnUBKvD3tE7KkidYNGhS1PM3-Q14Jq6lH2KacZLYeaqHfGg", "name": "St Mark Fine Arts Conservation", "rating": 5, "id": "ea2d4bac6d74716b33f456dff3aae0cc0b43cca3", "job_title": "Precision-Executive-Search", "place_id": "ChIJKbDEoXm_QIYRcRFBlp0dE8A", "address": "4901 Main St, Houston, TX 77002, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.483218, 29.7482286], "type": "Point"}, "properties": {"photos": [], "types": ["point_of_interest", "establishment"], "reference": "CmRRAAAAKw9W-Iss32NSdCgGiWo29_3KHf5vb_VdMOPDUYdQPTrDasIfFO2ONMxHzAmkWC5MFKGEco1qPvmdzztvUSK7a_GUGHwYJVuF4dqKbFxwNTZbmNrPBs74mcBNCKHG8byCEhBVsDpY8UuCZYse3pXPTqj4GhRx_P7mAnA8749ZGVoHkAWZQ5DZQw", "name": "The Nature Conservancy", "rating": "NA", "id": "90af6fb9fb926dde9f7103577cebc4150bbb1dec", "job_title": "Precision-Executive-Search", "place_id": "ChIJq-m4EX3AQIYRJkn4Lhccp2E", "address": "1800 Augusta Dr #240, Houston, TX 77057, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.42318089999999, 29.7345943], "type": "Point"}, "properties": {"photos": [{"width": 750, "height": 437, "html_attributions": ["<a href=\"https://maps.google.com/maps/contrib/106788706324997826205/photos\">Erika</a>"], "photo_reference": "CoQBdwAAAP1UvtRzF3ggJ66UMY_K30LgUqWBLsd70ilkTRc5FbyeYE9-SHkc6pjTJ1UWQiIPFTqcGr3MVJZS_ZTcnBTW3zZYjvFVj-ovelD1dURrEOSpS2cC9pkvlUfYbivV_b75JnFYI97uNl-QVC-dN02dYCaFFTm42CPj2tc6KGq9VT--EhAmwKuQrbIdxf8jx4b38xY1GhSqGHZx7nUR4XS4_DI8PRJvXEH6lA"}], "types": ["point_of_interest", "establishment"], "reference": "CmRRAAAAUkpy0E-tCxOP6J5MKrnqfc7ip5hWb4UguaMzjLHsjPsytmrreIke8evV78fL9hFy3TjXI_VxIk9AUQ7g8UDVanvfzffJ_jNqiojQVnKKS157ngg2bp9T2l0ctjDfigeyEhDHaJmd7u2XIbgDcjil3GX2GhS5GPerbmnsDSudG5qVyXQDXZDLQA", "name": "Student Conservation Association", "rating": "NA", "id": "1c5ea7722fc0d99e9f7dfca55f5d9078224d51d3", "job_title": "Precision-Executive-Search", "place_id": "ChIJQcqBXfDAQIYRErawO-goGj4", "address": "2990 Richmond Ave Suite #400, Houston, TX 77098, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-96.038102, 30.055621], "type": "Point"}, "properties": {"photos": [{"width": 984, "height": 985, "html_attributions": ["<a href=\"https://maps.google.com/maps/contrib/110279808588468038448/photos\">Peckerwood Garden Conservation Foundation</a>"], "photo_reference": "CoQBdwAAAC-b95z4wvj3p5NhZqfMc6-sHxOh__uywpm2PwjPe5AazGiyE0WoozHiItMckxiTzp4dgNUbfAS3KaoxkvqLhLzXLFzrOrcydviwOo9099ZTY1AQwfT75__vetPKTSQ8OKRD4HtPsUMeCwEt1Yzv3br3Y4D7XE0uyz2KECgKx9urEhCQ0HXzRviINTtkelO2wVWyGhRXWmOpNNeh9-X0f2WoRLd0HBL6FQ"}], "types": ["park", "point_of_interest", "establishment"], "reference": "CmRRAAAAKUfigJF3231LKc4ldGvQoQPZAMAkvltstO0DIPyvRjvWjh5s1UvJQG4U2rFb_BV5zL29ZIav7CYkp9aHbArMqHiUxgUslR8d7ZVSE_Z16ND0pOu0sVo9irRiygqAzrnIEhDIlVxaMhnKx_P6vI7KNst1GhRlpppBPccDeAUfuvJmZV6t8Ynm_w", "name": "Peckerwood Garden Conservation Foundation", "rating": "NA", "id": "e618a4c618cd67ce4f5fdc165f640220ab3b53b2", "job_title": "Precision-Executive-Search", "place_id": "ChIJmUR7pvHKRoYRIIl0o73bPGE", "address": "20559 Fm 359 Rd, Pine Island, TX 77445, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.64386449999999, 29.7515036], "type": "Point"}, "properties": {"photos": [], "types": ["point_of_interest", "establishment"], "reference": "CmRRAAAAlipxFrBnt2XO60vGjA9fVYm61TFMrjxub2D-MlxrR0vPax6jg-OdJB6PfW02AOBdhfD9v86aDeO9lJSwTRyjWGxAxxzeQKeg6P-nmGD3a0gWZe96Y9aRjRo_MvJHm8jiEhB6OPUNSt9DCho0g7T1F2EDGhS8_S31kOw_7iQtSf7PD-bzvuEMZw", "name": "H2O Conservation Technology", "rating": "NA", "id": "30c07988ef8dfc62dac712b9d587daa4a36f2539", "job_title": "Precision-Executive-Search", "place_id": "ChIJIWZRKeHKQIYRXxta3wOMGGc", "address": "1725 Hwy 6, Houston, TX 77077, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.5705632, 29.7714443], "type": "Point"}, "properties": {"photos": [{"width": 3024, "height": 4032, "html_attributions": ["<a href=\"https://maps.google.com/maps/contrib/108143329814504597326/photos\">State from Jake farm</a>"], "photo_reference": "CoQBdwAAAGuOL_pNsJrJ9wYPIKLTk3xkvTwajYM1ROo7BjRd8xx3X6SZx3crHEtlKgk53_RhoycMo_dkmDg3d9v17tcxbQfmsVPR_oX3b6I6ZkMfhSx27t2qkFC0Er33nHsIrIZ-3BLSgFZa1u57gIGbn7hTlZjXmGed7XeX8vGYUHBb4Mm8EhD6wEK2ifHd57jmmX-qsxPbGhTbw2CqHdJkwycUHnE71tW966xnxQ"}], "types": ["park", "point_of_interest", "establishment"], "reference": "CmRSAAAAPNhdOOTaX6dXS336wj7VFo1xyQcwmGNU5zTC_VqMQHfSTi5g0bmytkQ-0gvUq51ngfB9M-qlBjgZGUsfveGnGgcKz7UlzyrKUYjOMtACLxWHu0c77ppYbVZFKlPncWF2EhDFgfdtoE4Dndp1v4LQfCX5GhRPSy1szFB34Aydhdv-a6oTW8aSvg", "name": "Houston Audubon Society", "rating": 5, "id": "050a5458d86bdd1cee7b09678bd6256d0a20a73e", "job_title": "Precision-Executive-Search", "place_id": "ChIJlQOxwVDbQIYR2uX_TZl0TYc", "address": "440 Wilchester Blvd, Houston, TX 77079, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.56820189999999, 29.770778], "type": "Point"}, "properties": {"photos": [{"width": 1800, "height": 1200, "html_attributions": ["<a href=\"https://maps.google.com/maps/contrib/108765250995932379967/photos\">Audubon Docent Guild</a>"], "photo_reference": "CoQBdwAAALXeYquisTY3yGXT_K5Mr0STTWnCXsPA03j8U89ohoVf_XQXzM9ZZ5-etfQPIl8MdcyLtCPw2hD-pe2jsR-upOY1kUSi95fGyCFMJ23dQQKXZFcCoeYVLCoLvhIL436ZeqGsIe4NUvwvVNGkRjyDXBxuKMYnEa4LJO2R5CDkPPAuEhDd7mPNIPqb57_d8tlwrJh1GhSoA_5vpNgEhADLW627k3ReEtdg4A"}], "types": ["park", "point_of_interest", "establishment"], "reference": "CmRSAAAAaGr1Xw97fUl529E57Uu_n8ole6a9RzmFdkUFUZ-AhgCWhh9xUoAVMhvtAcRWx7Pg1Q3RTQQkTWNAYZcyd3uiJmQ76mlCdJYmnuhV9XddEW6kej8wCVAdbMTJdy5CZKrxEhC2VyGhG4DFhcjI501pnuJcGhTRh0-GQCoco12aFFHrW99jDy2bcw", "name": "Audubon Docent Guild", "rating": 5, "id": "7ddd5daf76cc4979e2ba6b062322d1c77d5d1c07", "job_title": "Precision-Executive-Search", "place_id": "ChIJI9XyNFHbQIYRtwHb8EtTpeU", "address": "440 Wilchester Blvd, Houston, TX 77079, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.44932349999999, 29.7803218], "type": "Point"}, "properties": {"photos": [], "types": ["point_of_interest", "establishment"], "reference": "CmRSAAAA75qt2h9zsMoNG8d37xJ_wnnIOeZX_HhGEhSyTypVCijz7_MVi6armqvsDsPX710IZYtzzt0V2Q_84TAVAALTnJ_xQV05LVwbHmNJJ4AZf9nHkwySxM6RmjwVsD9F3RjrEhAca_cnkvJ3ZyIPxXyXYup6GhRZgEW5K9xcLDc2cxBGq5VSkzAnGQ", "name": "Coastal Conservation Association-Tx", "rating": 3, "id": "7258b034e119f31e82320bca6e72781ee9f79d75", "job_title": "The-Music-Teachers-Network", "place_id": "ChIJcekacM_GQIYRPzL13cgQrPk", "address": "6919 Portwest Dr #100, Houston, TX 77024, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.47039, 29.655454], "type": "Point"}, "properties": {"photos": [{"width": 5312, "height": 2988, "html_attributions": ["<a href=\"https://maps.google.com/maps/contrib/101184977609161362375/photos\">aug4</a>"], "photo_reference": "CoQBdwAAAGIKTp_9Q8zIF3TCjazvumEj7HRDfyYqRVxxcJeHIj5X6Xae3KvgKzzAHEgwPrBYlk456M-MpzAtndbR1BSSjiZtF6Er9dpPX8O_RP6D9NHnUJluw6IjYNu0N0JUXvQTGMHyGagOaAUHHiNhOUFqCOZY5RXAapZtAo_1DBCNU93nEhB5xY6OJ_6OpZOsSgB3E88zGhTqCRa38WBD56lsVuDmieL2EsD4NA"}], "types": ["park", "point_of_interest", "establishment"], "reference": "CmRRAAAAP8XKahbMW73rY38TvvMunMKezy7gtBsR2GF1Y8IzBo--fRI30AG5FVDEvohKgnNnxZtjAvy15twAoDVEMHt_xhAqO_m_hrmENUmIZCzeLl0xJiWVM66upo2_bASOIXG8EhAZKC8e7SQZZlcEefg70nVHGhTYmd-jCZk2TH23wGmXbFKWAv7h_g", "name": "Willow Waterhole Greenspace", "rating": 4.3, "id": "0127506e8071350c2d48f0ca56e939045297a0f4", "job_title": "The-Music-Teachers-Network", "place_id": "ChIJR6_2zTzqQIYRsA7wExgfDWs", "address": "S Willow Dr, Houston, TX 77035, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.4003322, 29.7388505], "type": "Point"}, "properties": {"photos": [{"width": 1136, "height": 640, "html_attributions": ["<a href=\"https://maps.google.com/maps/contrib/117056878997299689379/photos\">Marisol Brown</a>"], "photo_reference": "CoQBdwAAAPahnL1ndlU2p7oYvpIJaJY7EINf2-E9OKjAojWwsTI94mB2lm678EstjfCHg11y4lqpxWivMkR2wYaWrdlpzqhT7vP22za4ZNkKYJ9SO-H6zigrFFqRRJ4ch3r54cDsqA9vJ6ZmW-Bkcd-sCxM4Suq4TwjUJ-XrsD9SSbYxaSGqEhADebjVIuTMNoDFlGLAtUbVGhTmUgtmLkzcMqlnv-mDzqJboUHByg"}], "types": ["point_of_interest", "establishment"], "reference": "CmRRAAAAajADpfUzvIFy0r-NDdaduxXZbeQqDUuZ7GjsKggh6Td6Q7vXj5z8rfuFrOgzURY2fOy7HpmMrVm_tQ9JZCgts1xRlEQjMoWpPPQGhX-axMk24hSbGep9ESTklZiT0-DIEhCclR-d3JiiRr8oKngvUTYzGhQTjM8ISruZSivnNQHIFTQSe9Dejw", "name": "Masters Fine Art Conservation", "rating": 5, "id": "a462c2eef4e22ea319485ae7b84f3d20756cbdd1", "job_title": "The-Music-Teachers-Network", "place_id": "ChIJp8u2bZvAQIYRbosnWz6cVmY", "address": "1612 W Alabama St, Houston, TX 77006, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.3876169, 29.794149], "type": "Point"}, "properties": {"photos": [], "types": ["art_gallery", "point_of_interest", "establishment"], "reference": "CmRRAAAAj6GT1S2KoXMf9HSuJuOMkPr4-U3U2mSfU0SUSQRtYIwXuFBsck1TYm2JdlqlW1BC-vW4advr4EmSFWjQdkhgLqR2BdRRIaiI7uMJrcBTgfRP0GWlGT4767V877uhn-01EhAXi-ODS8zAhw8YGXNaMwWZGhRs4_wlrjnXqUQZ1YnThqgjRgLZCg", "name": "Whitten & Proctor Fine Art Conservation", "rating": "NA", "id": "883a8c5ef35ab28e1630235ad65a6b16506a67fa", "job_title": "The-Music-Teachers-Network", "place_id": "ChIJ8YuXE6K4QIYRn1SF1hazFEw", "address": "1236 Studewood St, Houston, TX 77008, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.3858767, 29.7300997], "type": "Point"}, "properties": {"photos": [], "types": ["point_of_interest", "establishment"], "reference": "CmRSAAAAJir4vlWkN2HiwJpSMhPH1K9KEsyDW1LObeJO3NmcPt1fvDFZfF1s9CDcekskBTsCz3_F6r1BY9D6BdJap51G8roJeKohWGWc0cQ7aAFj_zOhtVNqJTYmLRToQIaY0v1DEhAwcDQaYLRxxdFrWKlEAfAxGhSd41MFXOwhrsn3uanAe5Yb9-MfdQ", "name": "St Mark Fine Arts Conservation", "rating": 5, "id": "ea2d4bac6d74716b33f456dff3aae0cc0b43cca3", "job_title": "The-Music-Teachers-Network", "place_id": "ChIJKbDEoXm_QIYRcRFBlp0dE8A", "address": "4901 Main St, Houston, TX 77002, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.483218, 29.7482286], "type": "Point"}, "properties": {"photos": [], "types": ["point_of_interest", "establishment"], "reference": "CmRRAAAAxdcitcPdyNB4eiC0YWu7OeVNjcuLY9ZUmW-4cAKjVpV4VpLQwFLP4slYCYzxE5cLYjHGaRwB36d614Xxichayqo0WFa0fYCsJKPVs1XcGK-xvspgaNYKgV2p2tWNu1_qEhCTwYAI-dVNpaer5tjfq_o3GhRU0AXpsQKmsAqZjt_udZ4nSIKfxw", "name": "The Nature Conservancy", "rating": "NA", "id": "90af6fb9fb926dde9f7103577cebc4150bbb1dec", "job_title": "The-Music-Teachers-Network", "place_id": "ChIJq-m4EX3AQIYRJkn4Lhccp2E", "address": "1800 Augusta Dr #240, Houston, TX 77057, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.42318089999999, 29.7345943], "type": "Point"}, "properties": {"photos": [{"width": 750, "height": 437, "html_attributions": ["<a href=\"https://maps.google.com/maps/contrib/106788706324997826205/photos\">Erika</a>"], "photo_reference": "CoQBdwAAABAA8I9sygqGHJdw8S86jCsteps3SA_OYzLWC0qiaxFb31g-IlEEQiHbIyNAtjzNJkQp6kweuGe464BWS2iCnrVCPV4tF7f8LGgk6QRjlEOExzXC8hVRBW4wM4YA7_FPZAQ-7XTFBhGtB1PV811_PTEHYR73YvAzSJmF7LHdmbAcEhAinJJsK3FzNMAu2RRD693UGhR2q7778Q5FC_ZQ5iYncak0grYX8g"}], "types": ["point_of_interest", "establishment"], "reference": "CmRRAAAAwQE2rwFp9n_mh5B9T19Td9LulakDNNc16eWENkfvJzyF949IbsAf7E4712Tm5f1MNfQWEjwKrxIeXDM0m0Ebu6w-TUagsQTiHcZ9g2r0fR7HwO9jhIgDbBfx_jc317cJEhBlUMF97-qk2iSX3_N1ThsXGhSf2iDLSZzXDa3WisTq4rRk87paRA", "name": "Student Conservation Association", "rating": "NA", "id": "1c5ea7722fc0d99e9f7dfca55f5d9078224d51d3", "job_title": "The-Music-Teachers-Network", "place_id": "ChIJQcqBXfDAQIYRErawO-goGj4", "address": "2990 Richmond Ave Suite #400, Houston, TX 77098, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-96.038102, 30.055621], "type": "Point"}, "properties": {"photos": [{"width": 984, "height": 985, "html_attributions": ["<a href=\"https://maps.google.com/maps/contrib/110279808588468038448/photos\">Peckerwood Garden Conservation Foundation</a>"], "photo_reference": "CoQBdwAAAFLl-E4drBhrEjTVp64rOJf1zKwQ6Eb9PZXQDQBjce_E0zcqPzyX8qELnoZwzJL2P2sMwEyrckl2K477Rph2POkb6PCg8q1n-uxK3Lj1jqCZI5-fJEytvf061Skq1hVL8FE6tXLfPuFrl3jSW_LLN3LEPCQO7mO7qQsrdhtveewzEhCKTBGG567CQLTybVm9Yg9WGhSLgsobzcRaZ1pKwTLP3SXX6tIuoQ"}], "types": ["park", "point_of_interest", "establishment"], "reference": "CmRRAAAAY1CIsyRFwbB1C80USFYTQcW56KaOzsQ_rEjIk2KMGtEoc4NIb5UWoadGkgkUGACtD7K4ZhTJcITPMdVqarzKtskcROaxj4gIhvKHtmhZ9xtaSPCE9swLpSfEHFeAcs4sEhDu1-c-JKszkj3F3Hu5fm_8GhScbZjJ_Mi7qIPMuMkgIadc7tmeHA", "name": "Peckerwood Garden Conservation Foundation", "rating": "NA", "id": "e618a4c618cd67ce4f5fdc165f640220ab3b53b2", "job_title": "The-Music-Teachers-Network", "place_id": "ChIJmUR7pvHKRoYRIIl0o73bPGE", "address": "20559 Fm 359 Rd, Pine Island, TX 77445, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.64386449999999, 29.7515036], "type": "Point"}, "properties": {"photos": [], "types": ["point_of_interest", "establishment"], "reference": "CmRRAAAA7MIEBZET5wsVER7psQ_Z9IfFBiwJYvE5MW86PAkqZVNB9XPLgoVDqKH6-VW8uDntKwZYt88JcigjgPZ9XfRSYkmV3WPtkDTLusH--1nXo1C6TLjVrp0vxUikh223ipcqEhAHPHkQyLv-qDuKAfVTJAqXGhTdjNQE4oR5Vk40SPfpMolTTcY5Aw", "name": "H2O Conservation Technology", "rating": "NA", "id": "30c07988ef8dfc62dac712b9d587daa4a36f2539", "job_title": "The-Music-Teachers-Network", "place_id": "ChIJIWZRKeHKQIYRXxta3wOMGGc", "address": "1725 Hwy 6, Houston, TX 77077, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.5705632, 29.7714443], "type": "Point"}, "properties": {"photos": [{"width": 3024, "height": 4032, "html_attributions": ["<a href=\"https://maps.google.com/maps/contrib/108143329814504597326/photos\">State from Jake farm</a>"], "photo_reference": "CoQBdwAAAJ2XKQNVo4YKrz6WB2dXYl-nxry96yezSvFOOElOLXyCOEiiBVf6p-EQY5PFMHXY3YhO3rDA8euHe2QCLUDk-GwaYZ4xO8ZKCeuPEDVbtXYBMvv87YIwv01prXzZCQtvFTnk6FaZNETHFFbn6WqHSLkIpEYNW8J9__23ZOMXVr_6EhCtWvGZGxqQEcxfaOELQ_86GhSIECaw2xEXSvaVpt3L4KJIVamaxQ"}], "types": ["park", "point_of_interest", "establishment"], "reference": "CmRSAAAAp8uJPS3N8bBuFcQofR9vwwlIzUDQwZvuSbOUDzjsJAawV3ZOIt4mQgUIgPtSScXjFiczbj5albo3NuGmV7OrKCs7W2ln3xXNQ7byNfbjGVM8LhcJ1HU7PPpsTx178etMEhAMa7NTveQHIazAFKn4iQEpGhTCZ3i7_q6bV1NoEoFjzFWEuCRhCg", "name": "Houston Audubon Society", "rating": 5, "id": "050a5458d86bdd1cee7b09678bd6256d0a20a73e", "job_title": "The-Music-Teachers-Network", "place_id": "ChIJlQOxwVDbQIYR2uX_TZl0TYc", "address": "440 Wilchester Blvd, Houston, TX 77079, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.56820189999999, 29.770778], "type": "Point"}, "properties": {"photos": [{"width": 1800, "height": 1200, "html_attributions": ["<a href=\"https://maps.google.com/maps/contrib/108765250995932379967/photos\">Audubon Docent Guild</a>"], "photo_reference": "CoQBdwAAAEbo4iK5u6daGIP8X4XCmAiJHYx6pS7WwXu0y1YzAPuJZHOXrtuG8lpbhy8TEEUxiRz9upOAf_4pmfWOrsVMbsOFlkT_4Pz2Ej36e580E3MaV-rxF06hr0QyXN92vxQYugQBYEDoIsmu2Qnij7QF3qB0yJf5JtnTyao0UxqNELViEhBfQ6UuFZYD5H_ZdjaAibW7GhTPp-BdutnJW4v7rq9Oz53uWC8dlA"}], "types": ["park", "point_of_interest", "establishment"], "reference": "CmRSAAAAjqgO4C2DDGx1sLMw0ICDhsAfmc1dtlbsGkzxHO4Px9PGh048wuJlmyvh6J2R1NV8v9n0yq9V96Dnl9P56E5GVCHFvx3qiNIuYdNMLQZxtdUuTGukSAa4GvQFfON_QNKeEhBJQ4PAXZcOqB7uDDdzfgIxGhSUpMlXNtqB8g3PKlaq05t3qXuutg", "name": "Audubon Docent Guild", "rating": 5, "id": "7ddd5daf76cc4979e2ba6b062322d1c77d5d1c07", "job_title": "The-Music-Teachers-Network", "place_id": "ChIJI9XyNFHbQIYRtwHb8EtTpeU", "address": "440 Wilchester Blvd, Houston, TX 77079, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.44932349999999, 29.7803218], "type": "Point"}, "properties": {"photos": [], "types": ["point_of_interest", "establishment"], "reference": "CmRSAAAAoXEf4ro1bu92cZ1yaDq8hCOTsOIqOhE9-5rmzks7TzIFR9NqYuYkXxTronFcobR9sLS4c6jtIoAXeKnkqRb1d6pN92-5cqw1pFyyVtq44r8rhTIX6h1DX_BAO0gnWSGQEhCX73u107ygxg3-2Tt9xNv3GhTNP3w7LfMueXkLaA2XlnVDDABE9w", "name": "Coastal Conservation Association-Tx", "rating": 3, "id": "7258b034e119f31e82320bca6e72781ee9f79d75", "job_title": "Enrud-Resources", "place_id": "ChIJcekacM_GQIYRPzL13cgQrPk", "address": "6919 Portwest Dr #100, Houston, TX 77024, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.47039, 29.655454], "type": "Point"}, "properties": {"photos": [{"width": 5312, "height": 2988, "html_attributions": ["<a href=\"https://maps.google.com/maps/contrib/101184977609161362375/photos\">aug4</a>"], "photo_reference": "CoQBdwAAANVfOZA0yoVxT70MjIi_TNpO9bOYEsiI1VeMCqIVkf991LKUZdmtNBf9j8B_dHw4ee2WefYtGb8DGufuF2iOYNdt_kyQfTYxtMQB89iorbp7Q6dmtGOSskGa3-KXSvhbn7_jGu_dMPMKKmKHYfkoz43HDbSq-rLgaAt76Yduq49_EhAOOCu1GocZNB0SBDFoiGJuGhQEZoep2vs5vkAtwb2yiEp73f43-Q"}], "types": ["park", "point_of_interest", "establishment"], "reference": "CmRRAAAAgz6-djntX2pi0X6ezwAmVBOo21C1hhC_dfcyztsqQzaOaEkM4pyjsF27ecW7yEne5M--WUT0d_sGoYfdNguj6Vki2LpvnXXgFHOnaKett2Vfgh7ull4ZrXY9dwuzuC05EhDtNW6UYfRiXkD81rRPQZuKGhRj111Q94l3TNJ6szDdZrE8y7hAhw", "name": "Willow Waterhole Greenspace", "rating": 4.3, "id": "0127506e8071350c2d48f0ca56e939045297a0f4", "job_title": "Enrud-Resources", "place_id": "ChIJR6_2zTzqQIYRsA7wExgfDWs", "address": "S Willow Dr, Houston, TX 77035, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.4003322, 29.7388505], "type": "Point"}, "properties": {"photos": [{"width": 1136, "height": 640, "html_attributions": ["<a href=\"https://maps.google.com/maps/contrib/117056878997299689379/photos\">Marisol Brown</a>"], "photo_reference": "CoQBdwAAADxtdijLFpaXyqSi-pJDGKLz0VSQQl4qcBpdgLMSNkIXcxRoNLZsTrCliqg6Be7awzTqXNKiexrCXiNetvGrBFwpxv5vfz2q4tn_8iNDJBmaWc4V6mSD2lxOf69NZdVrHDzxuLrLfRylTZ6_p5GGk0MUAUobYbTkafCmUw_MS-aREhAegJteqOlsVwdHBBVLC23kGhT9z-PxdryjGhssA5tJp7fLXObYdg"}], "types": ["point_of_interest", "establishment"], "reference": "CmRRAAAACm5gecoQnzsWs2_E4i0kjuz-SKP7vJomeId6v7I4qTHo4Zsu8hxU3p7pxzXSVRv0uSwBvEgCQ_oe9MiZ0vuZeuE2ZuSoiIdp6pEWMJaskYTrCn79sIQOVPZdD2OMM2I9EhBnIBet3Sb7KiUG4oix3thVGhRFkGycJQoglD2OrRoaur3vhj6NmQ", "name": "Masters Fine Art Conservation", "rating": 5, "id": "a462c2eef4e22ea319485ae7b84f3d20756cbdd1", "job_title": "Enrud-Resources", "place_id": "ChIJp8u2bZvAQIYRbosnWz6cVmY", "address": "1612 W Alabama St, Houston, TX 77006, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.3876169, 29.794149], "type": "Point"}, "properties": {"photos": [], "types": ["art_gallery", "point_of_interest", "establishment"], "reference": "CmRRAAAAvC_mePPFHxI71OzUqEmV1ly_xvK8ZOaTLgEPOJJUrNifFLW-LozQze5RU7h6D4hjX4uDz0DXvRSWDraROm-zFvyPG93KhPjBn9o6y9PhlMEbRWejis75iLjKpm6ad9peEhDMY7uIpIUAmLHgbtM-xe17GhTZuh-DBdL9QKt1UbnEpa_ViY432w", "name": "Whitten & Proctor Fine Art Conservation", "rating": "NA", "id": "883a8c5ef35ab28e1630235ad65a6b16506a67fa", "job_title": "Enrud-Resources", "place_id": "ChIJ8YuXE6K4QIYRn1SF1hazFEw", "address": "1236 Studewood St, Houston, TX 77008, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.3858767, 29.7300997], "type": "Point"}, "properties": {"photos": [], "types": ["point_of_interest", "establishment"], "reference": "CmRSAAAAazC23rCkF-pI-Ued6Yxb3VIpgUiBnNKmjJlEpApTq0nTqWYrpifRUV1x5fKRx1mRV4Jw3hEBFUzsYCrSQtK06FaVL6ZjU9gSMWlnhAAc6Tt8JDpYdhXk9mgppG4wvjnQEhAmkkmj7JKOFqeuMFBeJF43GhShVAyWTRC2kt_K8r5N-QyfIRp2lg", "name": "St Mark Fine Arts Conservation", "rating": 5, "id": "ea2d4bac6d74716b33f456dff3aae0cc0b43cca3", "job_title": "Enrud-Resources", "place_id": "ChIJKbDEoXm_QIYRcRFBlp0dE8A", "address": "4901 Main St, Houston, TX 77002, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.483218, 29.7482286], "type": "Point"}, "properties": {"photos": [], "types": ["point_of_interest", "establishment"], "reference": "CmRRAAAA3K0PsdicN_cHg0mApt_8TbXbY5meCcj_F0IGVG46qW0B4gNh_wze5r8_umQNE7cDlZU597duF0YqYfrYS5SotYdoPyUXKUGPSGRPK53r_cF9CWGiVKYyYZVJV6FLBvrREhAGB7C0H5jBhiSka4x-jlbrGhQTRqtTwo1HWNQgrvRNfcxhEis60A", "name": "The Nature Conservancy", "rating": "NA", "id": "90af6fb9fb926dde9f7103577cebc4150bbb1dec", "job_title": "Enrud-Resources", "place_id": "ChIJq-m4EX3AQIYRJkn4Lhccp2E", "address": "1800 Augusta Dr #240, Houston, TX 77057, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.42318089999999, 29.7345943], "type": "Point"}, "properties": {"photos": [{"width": 750, "height": 437, "html_attributions": ["<a href=\"https://maps.google.com/maps/contrib/106788706324997826205/photos\">Erika</a>"], "photo_reference": "CoQBdwAAAGGYzpGqthZtvpFyU9y6HnxwF-ZldZwc4u8nZn3AZRQzwrI1VFDFB4MbdvdLvt3L7VwJQ-lSL_REJrAJe84Xm63tm3jD2FsTLdHyNLp-AtbqQEjcARNqgqkM2EKwp06w0m1GWMjYMJQEDX1hQANMOJqLpuLEnGKyUO4V8b6V4JRYEhBmSYhl1g-QX3wyoPa67brSGhSW3D60n0fPNeJeSK-yQjx4EH5fHw"}], "types": ["point_of_interest", "establishment"], "reference": "CmRRAAAAPq-8BRiO7MW50KDTEJDBq8dn_jLf8pctgDj8p_jsuOoR66v1W7ttQj6fn0I4pyu5H_dB8M5zeD0RTPKamYbFbELnkWY4pRtpkHZ2hlJzhXWXIwroHCBIRmkJLM2lw8DAEhBrjpVn2y9YflrppVsiN94AGhSDzgduDhOvKvovDe61JId1ttk7Sw", "name": "Student Conservation Association", "rating": "NA", "id": "1c5ea7722fc0d99e9f7dfca55f5d9078224d51d3", "job_title": "Enrud-Resources", "place_id": "ChIJQcqBXfDAQIYRErawO-goGj4", "address": "2990 Richmond Ave Suite #400, Houston, TX 77098, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-96.038102, 30.055621], "type": "Point"}, "properties": {"photos": [{"width": 984, "height": 985, "html_attributions": ["<a href=\"https://maps.google.com/maps/contrib/110279808588468038448/photos\">Peckerwood Garden Conservation Foundation</a>"], "photo_reference": "CoQBdwAAALMxjLW8TzPIaA7Po5W-_SVfoCylhVfPNpbvQ7yTTAHX7Mh5Z9MJ59VjsiDByIM47ekevh9rzugmsOYQUnsjM3poBrA4ryWDtVcrG1wsrCwPHkYblIJBeV1QfOaB5nDiDHzTOwFnq_Qpg4vc0ARk6l4WACMVtIVfapoia3ic2S57EhDnbPw-1PYXoxUhS3G6P4QrGhSpUzT7FWxFUycDlVzPqWTQAlyCow"}], "types": ["park", "point_of_interest", "establishment"], "reference": "CmRRAAAAvr9bb8GnIkqjVTUidYKC06ydO4TPbVC6rcOQSYqETRkxqxxhDtHcEIRYBplOFgloBq1mpfhyVVDoaVarSMvpdCriflc8SUnpP8FLah2Bu4X0YFFAeSaQs865gkGBoaTdEhB-dhCXijvnVlGflHOHSnSCGhRekVFBYn94n3DbnxY_1-bMe2Wcww", "name": "Peckerwood Garden Conservation Foundation", "rating": "NA", "id": "e618a4c618cd67ce4f5fdc165f640220ab3b53b2", "job_title": "Enrud-Resources", "place_id": "ChIJmUR7pvHKRoYRIIl0o73bPGE", "address": "20559 Fm 359 Rd, Pine Island, TX 77445, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.64386449999999, 29.7515036], "type": "Point"}, "properties": {"photos": [], "types": ["point_of_interest", "establishment"], "reference": "CmRRAAAAVpSsF81ohaM_sUxlwQmNfs0nxI3kRtnB5NGQ5BjP13BcytTk51nsjGJvdvzEDp8cQ1Ep91WD4pl5o5dDZ_Uyab8v7T1KD23YED_tv-2Y141ioz9OeT-kPlPo9SHB6t4kEhAnZ1jHI6oqsw5dsM4L8wvVGhRM8hZl4KJGh3a4knPlgi2wKPF-bQ", "name": "H2O Conservation Technology", "rating": "NA", "id": "30c07988ef8dfc62dac712b9d587daa4a36f2539", "job_title": "Enrud-Resources", "place_id": "ChIJIWZRKeHKQIYRXxta3wOMGGc", "address": "1725 Hwy 6, Houston, TX 77077, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.5705632, 29.7714443], "type": "Point"}, "properties": {"photos": [{"width": 3024, "height": 4032, "html_attributions": ["<a href=\"https://maps.google.com/maps/contrib/108143329814504597326/photos\">State from Jake farm</a>"], "photo_reference": "CoQBdwAAAC6uI-TVlvA7gFbEMjTfGi3OV8CPdrV4W3bNFLuvqCusiFueUcasBSaGMtKuQUaxWBk-0CSBSoqGqxOfX43Si2tZUxcf-Gs5hInvHmC4WbvBKNrOspmpCSqE1J14KlaKyh9E_QIZemXjTTBkiJJrb2o3Y1JRBKwD8TBkvYbv9jIREhB7cb1zNL9RKHGiaAgecXdBGhRR67KPbZIFAntTbFslz1A-68DSDg"}], "types": ["park", "point_of_interest", "establishment"], "reference": "CmRSAAAAQCNZtLYDlod0UqTJGMhDC_h6v2CUaEGVQGHVQpmHZj4P8KkMvx8nkYVhoHY5APPLHEti1_IoKwui5BN1inimaWZJ_--7hlN3Bb8pS0CzpmUfCorkjcc9UzVHWyXh6IfXEhAWUAP5uzUnDZgJiuX5AfhqGhT_0rIFyv7hYO6N8kEf1e0NLJyEDA", "name": "Houston Audubon Society", "rating": 5, "id": "050a5458d86bdd1cee7b09678bd6256d0a20a73e", "job_title": "Enrud-Resources", "place_id": "ChIJlQOxwVDbQIYR2uX_TZl0TYc", "address": "440 Wilchester Blvd, Houston, TX 77079, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.56820189999999, 29.770778], "type": "Point"}, "properties": {"photos": [{"width": 1800, "height": 1200, "html_attributions": ["<a href=\"https://maps.google.com/maps/contrib/108765250995932379967/photos\">Audubon Docent Guild</a>"], "photo_reference": "CoQBdwAAAALmK95f86iGQ0jRpvMaXlu9jAYgFpTFgMXynOiW23XXTZoTv_f9qrkjGIQ-9kjAF_QNjnnMpxMcLTzLGXTcbgmP9oeAPOvCxgKW1bk6M7TJsFEFlKtk3GDiDFBG_9CLWJAv8zuVkYZmvBcGq7ib2vrCSKCAbeNsA_GZhyXe8KxTEhDSy5npBQX13Q6GwZX8zq5jGhQgk97qBlFncHR1COB1qJiSp8UapQ"}], "types": ["park", "point_of_interest", "establishment"], "reference": "CmRSAAAAmNXnmtvfaqmg8s1YGH_ufIkv6IVbzV0CTXxOd9WD0H8bN9NPfArvtEjko_mHsoHtSdF7_O9pWjwywlsbXbq9jeo8ncupcv5-xZJXiK7JmkpgAWmYmFhAdiauB9v7PdVqEhCXedCYN5rxJBFBHNYCLKqnGhRH1sGeLW0A6P1jM-d_7LF7V9VgVQ", "name": "Audubon Docent Guild", "rating": 5, "id": "7ddd5daf76cc4979e2ba6b062322d1c77d5d1c07", "job_title": "Enrud-Resources", "place_id": "ChIJI9XyNFHbQIYRtwHb8EtTpeU", "address": "440 Wilchester Blvd, Houston, TX 77079, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.44932349999999, 29.7803218], "type": "Point"}, "properties": {"photos": [], "types": ["point_of_interest", "establishment"], "reference": "CmRSAAAArLfKVjBtX9ay442eXmjRyVOr3X-fFeEXYldrfX2OWM1-KRSpgJLbupgVw1XOUQz8WCX6s0G5T7BHOY7J8qX53GO07EzK94JywsUaucpM_MIZAFzRvYz_Uh78lsjeyQgfEhBv0u1B_vMlzyVxYJp3O3_8GhTVb2PGn0gq4Iu6oPs8G8L0s1q1Hw", "name": "Coastal Conservation Association-Tx", "rating": 3, "id": "7258b034e119f31e82320bca6e72781ee9f79d75", "job_title": "Latham-&-Watkins-LLP", "place_id": "ChIJcekacM_GQIYRPzL13cgQrPk", "address": "6919 Portwest Dr #100, Houston, TX 77024, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.47039, 29.655454], "type": "Point"}, "properties": {"photos": [{"width": 5312, "height": 2988, "html_attributions": ["<a href=\"https://maps.google.com/maps/contrib/101184977609161362375/photos\">aug4</a>"], "photo_reference": "CoQBdwAAAC1eWHjRFHFwQ8Qnz7JicBzgkrT0aQXD7849A5D6afwtqha7AYU_Uh0rzF4uWGeufMwrfATVTcJ5KN3vo0jFVvdlAqxTzVfA_wjqteJD-mUaAFS3o2JDvGa0H4iDfLB1jPYDo5yw1XYjpOsrc2iLc1AuF4gyUf4h07um0KxAsxt8EhD-YcJFKWCp_ZoW4JJxBa4oGhTvt2OvqSvHrOW8WhY92VjPchcydw"}], "types": ["park", "point_of_interest", "establishment"], "reference": "CmRRAAAA-A7GdqKaATSG76eEfOg9CFTLyss9wtLgcP4dnLBZPTF0IMYZp-eOL5kCG9rjI23VWJdmIg_GE4vx6rjfRR6DZJO2rwqAqDKCW7_XTVDAKqX1ppTUWNGdq-Eu5viCLisFEhBoeZDvfqLfzN0umVSh7xmIGhQ33Ms1P1pJlBRL4GEJtxEb6HSPJg", "name": "Willow Waterhole Greenspace", "rating": 4.3, "id": "0127506e8071350c2d48f0ca56e939045297a0f4", "job_title": "Latham-&-Watkins-LLP", "place_id": "ChIJR6_2zTzqQIYRsA7wExgfDWs", "address": "S Willow Dr, Houston, TX 77035, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.4003322, 29.7388505], "type": "Point"}, "properties": {"photos": [{"width": 1136, "height": 640, "html_attributions": ["<a href=\"https://maps.google.com/maps/contrib/117056878997299689379/photos\">Marisol Brown</a>"], "photo_reference": "CoQBdwAAAI6Cc5jn31j3Sbos7bHa_fL-zZ09Mqv8GtbgYXE4KQxPrlEA1u7sU8R4mZOVtXAF_W4z9rp6S06iSa0SqbHyy6i9D6V8SbTQXbq7TDWbVPSQO_-FmTq_8iz19_3FlQwWTlI3Vc1dDXHSrpd2SpUJLslAUmrNJYrXmnPYEUHL6btmEhDXB9sgdyeFA2wxlon4bAmiGhSqxRQTLNjEvZN-f1qhR-_SwRsRww"}], "types": ["point_of_interest", "establishment"], "reference": "CmRRAAAA_xfLQAqOUrf92_NUZ2YRRNvsugvvVVV8c7J9Vgu_-HyEefm_4XQib40StKUsDCkk8tRqxlQTNjLTkVma7sKY_ZMvLQaXYHyroIiuapwgee4YaugsaAYRquFPTZeHpVO_EhDcK0_-mtEzKfT3mgTFFbHjGhTKGjIWuGzZVex1opVptwIw0MID3A", "name": "Masters Fine Art Conservation", "rating": 5, "id": "a462c2eef4e22ea319485ae7b84f3d20756cbdd1", "job_title": "Latham-&-Watkins-LLP", "place_id": "ChIJp8u2bZvAQIYRbosnWz6cVmY", "address": "1612 W Alabama St, Houston, TX 77006, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.3876169, 29.794149], "type": "Point"}, "properties": {"photos": [], "types": ["art_gallery", "point_of_interest", "establishment"], "reference": "CmRRAAAA5vfTByFN3mvyapiXxg6iU3EJh7r2DaCoBXJV5_OeYLkugKQ_T-5Jws2Ywt9HqYyjLj6jHAG1wYrzzhWJg9PrExtToT4CA2G95_0nLfTeT5iC9C-fY-ietu1YPRAOE8MgEhBuXI9aWQGsuyLlpbyn7xReGhRqZC5-5tEiHdeQLzCFoKZP6UFJuQ", "name": "Whitten & Proctor Fine Art Conservation", "rating": "NA", "id": "883a8c5ef35ab28e1630235ad65a6b16506a67fa", "job_title": "Latham-&-Watkins-LLP", "place_id": "ChIJ8YuXE6K4QIYRn1SF1hazFEw", "address": "1236 Studewood St, Houston, TX 77008, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.3858767, 29.7300997], "type": "Point"}, "properties": {"photos": [], "types": ["point_of_interest", "establishment"], "reference": "CmRSAAAAa_NcWUWrXgvK2_giijUk1qFhMgLQ8xanGkKlhX06FL5L8mQzr2K5FOKGoM8pVxVK6uSvMvQm0M4hchCqn4Vd-5bSKe9jfTIwX-6Q59OTWLEt4hm18F-r6Ay1q9pemxDOEhAwuUmnfwkCYzqzAOtvXtr2GhTyWQ6SGP_0vw3BfKq8ajr56w2xFw", "name": "St Mark Fine Arts Conservation", "rating": 5, "id": "ea2d4bac6d74716b33f456dff3aae0cc0b43cca3", "job_title": "Latham-&-Watkins-LLP", "place_id": "ChIJKbDEoXm_QIYRcRFBlp0dE8A", "address": "4901 Main St, Houston, TX 77002, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.483218, 29.7482286], "type": "Point"}, "properties": {"photos": [], "types": ["point_of_interest", "establishment"], "reference": "CmRRAAAAM_TpbsN8Y-pmiORtEIc7zkuBp30EkpL_5tXJ1u2g2LalPxZbOJKIhvaRyQ8CtJ-cFZZz0oK20oKhPg7Pc8SPKZvHjnm4QFq3U71uMxgcX7E6twL_PWYeRQwfBw0VNQGeEhBw82M4pIMo-GJCu6ZiknD4GhS6uTzKwdUoXayd6BhPHNWJdk8KAg", "name": "The Nature Conservancy", "rating": "NA", "id": "90af6fb9fb926dde9f7103577cebc4150bbb1dec", "job_title": "Latham-&-Watkins-LLP", "place_id": "ChIJq-m4EX3AQIYRJkn4Lhccp2E", "address": "1800 Augusta Dr #240, Houston, TX 77057, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.42318089999999, 29.7345943], "type": "Point"}, "properties": {"photos": [{"width": 750, "height": 437, "html_attributions": ["<a href=\"https://maps.google.com/maps/contrib/106788706324997826205/photos\">Erika</a>"], "photo_reference": "CoQBdwAAAC6YP79J5xI0BL2tVYfbygGxHDZzV4odMufI2yUUoQwCSKEWyOLEvnrciumlcivoOUkqIFhChGpHNOr_iQQs16cYi9xU39_Lo4XZJmz58cUqJ7SG-2Ef4pt1-gZ-zFaKfKKwkol2n4Lg6-rUqMqCH_ofOZQvrbEhuq7ZCToDbvrVEhBWV7R3lBg0JM-SNgTOXT2oGhRw-uMxygyL1wOnFEy_X3zEXIAcBw"}], "types": ["point_of_interest", "establishment"], "reference": "CmRRAAAAVw3qwlzV0HnlDT7ieqrMCyBvGn6hpkBxH3HXp20bC-VFThC3BVL_wOJe-u_-a6yCtGP5kGzx9P14f01_HfuFLpPyKBtpWCu8dsFNiejEuYKm1MiEs5DiUcJe_3S__CIcEhAOqdELkJQh48Gzyvfw0v4gGhRv1jPH6p12Eh9DEC_ZG35J53bz2g", "name": "Student Conservation Association", "rating": "NA", "id": "1c5ea7722fc0d99e9f7dfca55f5d9078224d51d3", "job_title": "Latham-&-Watkins-LLP", "place_id": "ChIJQcqBXfDAQIYRErawO-goGj4", "address": "2990 Richmond Ave Suite #400, Houston, TX 77098, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-96.038102, 30.055621], "type": "Point"}, "properties": {"photos": [{"width": 984, "height": 985, "html_attributions": ["<a href=\"https://maps.google.com/maps/contrib/110279808588468038448/photos\">Peckerwood Garden Conservation Foundation</a>"], "photo_reference": "CoQBdwAAAN0JRiuh6YSTH8NB0VAnVC87JEOmHeqOoR5kB0CQo2JlYyBaPFUaZrj9Uo7egxDxUSTJkdT7JTXwKN7XSdvn9SXL8wKq2qVu2KzHUA7_jyzdk8yMm1nTp_euCKRX6Z9K8bbN5cNgkaBwsWA2qGswCcYBJtA40YrGiPmeBc4p8u_0EhCw5_36D7AKdx8-oz7vcXhkGhRid-6_1kwzKKwjrttISuNOOtmu7w"}], "types": ["park", "point_of_interest", "establishment"], "reference": "CmRRAAAA8IbxPVNwYktd4RESPTUU6zssrDFW0FqsQ2o-l0LVcTzRZKAYQ-zF9NW6wlFtXeYsPvxfBBIUswi1iRFLGwNgFf5JEnWesssLRHC311A6C99RV79hS7PdsPkeL8u3b5NpEhC5IQJKl5OgtxumxTszraVVGhQwufFz_n5NFWrLNXNoLppWZ60vIQ", "name": "Peckerwood Garden Conservation Foundation", "rating": "NA", "id": "e618a4c618cd67ce4f5fdc165f640220ab3b53b2", "job_title": "Latham-&-Watkins-LLP", "place_id": "ChIJmUR7pvHKRoYRIIl0o73bPGE", "address": "20559 Fm 359 Rd, Pine Island, TX 77445, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.64386449999999, 29.7515036], "type": "Point"}, "properties": {"photos": [], "types": ["point_of_interest", "establishment"], "reference": "CmRRAAAAdL6SMnFexvR8BIXSIzyX8Twr_Q8-X24ALXHpAqhqEnHUODho9YnsqIiBTsJhVSx7ojSC6bqm2bouJylXSBjAyWD762IkUc8sFPnnmy6_9SYaUucKHNuR91WlHdj1M73VEhAsid3eJL4qwQaHBlz7dM1IGhSA4o0lTbDy--uLRhVa2Y2sJng84w", "name": "H2O Conservation Technology", "rating": "NA", "id": "30c07988ef8dfc62dac712b9d587daa4a36f2539", "job_title": "Latham-&-Watkins-LLP", "place_id": "ChIJIWZRKeHKQIYRXxta3wOMGGc", "address": "1725 Hwy 6, Houston, TX 77077, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.5705632, 29.7714443], "type": "Point"}, "properties": {"photos": [{"width": 3024, "height": 4032, "html_attributions": ["<a href=\"https://maps.google.com/maps/contrib/108143329814504597326/photos\">State from Jake farm</a>"], "photo_reference": "CoQBdwAAANnmtYulcspRtu7ygwAccmSf-zwscdRXlfn38Y_WUC3sZhyLYb-PBQTGv1rdRC0Pe4HilHW5xyHf81nVhnTVOAG41JuQMuXjL3qEtYzFqLgG5hVa95_IeIeX2h4ur-RZWShQhtC-Y1ZJTLG23ITZUIbJlcBmDeJdPt5A6_owbHzvEhAOKgGc6scO-wybKDDGWn_nGhSB_TQii5NeSXzvIl2iyrAXklQ4Cg"}], "types": ["park", "point_of_interest", "establishment"], "reference": "CmRSAAAAFeGIbOu9YX4qs5ub0sDUtTLU1r1U1Gz4jUYUi1Z5PM5m6sMa_gA4k6q6oIoJQdlqAaOX4Vdr9M_jZzS_pfw2FbZxLdAYUtW6oA6VkpT3Xlt3CqxN0u3pqE6o4ZyhagN6EhDZWglzmAVJbGX0YLBwOyypGhQ9U3p4iD3w9bHjo13askC9BzeSkg", "name": "Houston Audubon Society", "rating": 5, "id": "050a5458d86bdd1cee7b09678bd6256d0a20a73e", "job_title": "Latham-&-Watkins-LLP", "place_id": "ChIJlQOxwVDbQIYR2uX_TZl0TYc", "address": "440 Wilchester Blvd, Houston, TX 77079, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.56820189999999, 29.770778], "type": "Point"}, "properties": {"photos": [{"width": 1800, "height": 1200, "html_attributions": ["<a href=\"https://maps.google.com/maps/contrib/108765250995932379967/photos\">Audubon Docent Guild</a>"], "photo_reference": "CoQBdwAAAJ03p5XFClSlk5wz8_5vCsc0EEVDNdCiFP-zc3u5ieTORldLLJkipv83kEC4SK1p1InKRrs14JnwHQQdsT9wXH6mKZMzcugaAu5t3iIbdq5aFZtX2XlE1JTg4iQRXr1L0Q8tQZ9ivaYqZA1F7qLEXH8I3ESouM9hkWoGmcYUg1ALEhBWHESkC31WtAwFW4TVNjh5GhRiaADzoEBc9gyp32pqw0ei5_-l-Q"}], "types": ["park", "point_of_interest", "establishment"], "reference": "CmRSAAAA1IcaN6LPDK1IBUK_krbeWoWWHrsYhjsVRI57-kZqjo3bFO_QbPnkqqzes_jfGjHY0K2LZc4_hlFAaykKnDM_TudkoiZLnY-FxDJxJFqu2bofpPrMD3k_PZX0qvY1gcs3EhAR0erXZSBK-oYiSt-8C9IsGhTIN462jVykC80_aHDrPpEMvZ5zpw", "name": "Audubon Docent Guild", "rating": 5, "id": "7ddd5daf76cc4979e2ba6b062322d1c77d5d1c07", "job_title": "Latham-&-Watkins-LLP", "place_id": "ChIJI9XyNFHbQIYRtwHb8EtTpeU", "address": "440 Wilchester Blvd, Houston, TX 77079, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.44932349999999, 29.7803218], "type": "Point"}, "properties": {"photos": [], "types": ["point_of_interest", "establishment"], "reference": "CmRSAAAAWzTIkjBEq-58BcOfpbC6aqUBPuOnPycSwec_DbVcL5Ysm-oEXMv57kMumXSDwp5F8Juo6_pbwH6UpcDCcQpbXG0kJo7T-GzH08juQgD-FLPcPZJfkJb826YYjltvIFMAEhCWsLZ94QwLDKvM_oxjotWCGhTPb31WWUlCNPT55uHFMqb2ZL_CrQ", "name": "Coastal Conservation Association-Tx", "rating": 3, "id": "7258b034e119f31e82320bca6e72781ee9f79d75", "job_title": "American-Technologies-Inc", "place_id": "ChIJcekacM_GQIYRPzL13cgQrPk", "address": "6919 Portwest Dr #100, Houston, TX 77024, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.47039, 29.655454], "type": "Point"}, "properties": {"photos": [{"width": 5312, "height": 2988, "html_attributions": ["<a href=\"https://maps.google.com/maps/contrib/101184977609161362375/photos\">aug4</a>"], "photo_reference": "CoQBdwAAAF9jq76c0Ze06tsionRMZVW0Le7tn9XNLValcZrM-vJbad7zqsL36265m9ISl-5AeH59xp3WvTmSbuEILe39jjNK3EZqM37RnqG4wEnEdpVCPe589-sWwti_2IlvNmNHND4cC_XAWUF6QG_yRfwEnPcqjH8ehDLlp7lxxBSkObw2EhDzczePKZe3qhU0JjttYAaGGhRNWuOlnheW9ivDNzaX-6WKca9Psw"}], "types": ["park", "point_of_interest", "establishment"], "reference": "CmRRAAAAZFXr7zjlP7aURLdSiDLCUkqIMTyc9C71PFTO6_j5C3dD6UrfMQaUqR0rQQpy4ebfNmkTfIAif8GJxDQ9P3qAk0W1uBGt9v0yIZoRBvrVw2ZdXGjzVlLO6xOWYO_EhvVcEhAD4C4hAqFkZN-GG9OCpinnGhRpHs21a6Fk5fjRSPpDI_yuI2ry2A", "name": "Willow Waterhole Greenspace", "rating": 4.3, "id": "0127506e8071350c2d48f0ca56e939045297a0f4", "job_title": "American-Technologies-Inc", "place_id": "ChIJR6_2zTzqQIYRsA7wExgfDWs", "address": "S Willow Dr, Houston, TX 77035, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.4003322, 29.7388505], "type": "Point"}, "properties": {"photos": [{"width": 1136, "height": 640, "html_attributions": ["<a href=\"https://maps.google.com/maps/contrib/117056878997299689379/photos\">Marisol Brown</a>"], "photo_reference": "CoQBdwAAANcCx6vVS1E0_zZI67NIt93FFk9wAiYbad6vjE2hQPcj3KnTDtoPKRZbCYE0UErWHtcD6Mq7_SCyego72MfY7p6lM6Yg0KdsCblZKGmL0YFNXABIzuIxVSyh7ID19p-ECtKhULQyG6LVE2R89Lsg0Q0Jn9RQGuMUcSUz2nIDOxgdEhA3F91XhLoF0ab806NFzv2kGhQ6X1a3dPqkAQftJhYRw1ed8qDFmA"}], "types": ["point_of_interest", "establishment"], "reference": "CmRRAAAA-7_FZuCL18QQV-ZyRBaCWS2oPQ-63Qca-yRAE7c3VX6sMpq78AsZf-pzjZS_hEU3Fc0wU-sgoihoElKU_hKukf-GIbMwBKLFpN1ozCeNqWM-v6_2-HlpsIzLZWYAU-o7EhAtEMXXjsQJWvaiN7AHv0qWGhThg_pC1C259LVsqxA0HeK08oegXA", "name": "Masters Fine Art Conservation", "rating": 5, "id": "a462c2eef4e22ea319485ae7b84f3d20756cbdd1", "job_title": "American-Technologies-Inc", "place_id": "ChIJp8u2bZvAQIYRbosnWz6cVmY", "address": "1612 W Alabama St, Houston, TX 77006, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.3876169, 29.794149], "type": "Point"}, "properties": {"photos": [], "types": ["art_gallery", "point_of_interest", "establishment"], "reference": "CmRRAAAA_7Kb3L4qJ0_A9JSJXbmn1rqXc11jYoKR_V1gtpf46tsJE08fHQlP0OUtz6aAxMnclF5MklLXgC8yaFAiJQUdY4sUF0mTeRyG60G1HZz93FtYBvTDjGqbkbRjyymtDO5uEhD0Lf9jpbFPNSxK0Z95wLIcGhSgC6MgQSiuYJ9qwoAc_gVlwj6N9Q", "name": "Whitten & Proctor Fine Art Conservation", "rating": "NA", "id": "883a8c5ef35ab28e1630235ad65a6b16506a67fa", "job_title": "American-Technologies-Inc", "place_id": "ChIJ8YuXE6K4QIYRn1SF1hazFEw", "address": "1236 Studewood St, Houston, TX 77008, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.3858767, 29.7300997], "type": "Point"}, "properties": {"photos": [], "types": ["point_of_interest", "establishment"], "reference": "CmRSAAAARSUImpbXNwp8lWywsMcNL5Km377ETdJglAoqBDEoItv14Oj5Cser8UEEP6pRtLLrazMl-rq9AnfUEnnBm6eKGB8Cp0FPotPU2qTIFIpHt3wggc-skLO837wkn7fVBBK_EhCpElINSCPJcfJlU-7TIbv-GhQrlgo1TrFkE5Cyx7SQfSaGgeDSmg", "name": "St Mark Fine Arts Conservation", "rating": 5, "id": "ea2d4bac6d74716b33f456dff3aae0cc0b43cca3", "job_title": "American-Technologies-Inc", "place_id": "ChIJKbDEoXm_QIYRcRFBlp0dE8A", "address": "4901 Main St, Houston, TX 77002, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.483218, 29.7482286], "type": "Point"}, "properties": {"photos": [], "types": ["point_of_interest", "establishment"], "reference": "CmRRAAAAyC4xr20yaWHDyJ2sAZjt4perijBUR4yQMNXlfyy6t5Kn_bi9iJxBe43I488aAFlgpyBvRtqn5LYRs0ZTKpBkAMjylLwzKwcDKeTq1QZmmW5C0x0BbAP9PLtEQJfRkCcFEhD7ha3FNwj_H26Cu-HQcki2GhS_92mrLOYZg3tOOY9R-Y8Npjjmxw", "name": "The Nature Conservancy", "rating": "NA", "id": "90af6fb9fb926dde9f7103577cebc4150bbb1dec", "job_title": "American-Technologies-Inc", "place_id": "ChIJq-m4EX3AQIYRJkn4Lhccp2E", "address": "1800 Augusta Dr #240, Houston, TX 77057, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.42318089999999, 29.7345943], "type": "Point"}, "properties": {"photos": [{"width": 750, "height": 437, "html_attributions": ["<a href=\"https://maps.google.com/maps/contrib/106788706324997826205/photos\">Erika</a>"], "photo_reference": "CoQBdwAAAHWd4-sdLKdnTOLg_z5HQXPmAH7V5ls8ZMKrQ4Uh8p4DjuUrc3UIwx8LdGhRd5ceiEoV94Xr0XSFoD_kA-u1OUTH6pFYw7eoXk7wBW-83773ITfvAlQx5vrASQAiflBknEdTrkaE-IajQF4HmMHpcjOgLwDhTHZpwYOVvrXCU3GzEhCF6CDRpSGtGulf5XJojATgGhStJmbM6g_z2zRU6J1XXmSmk2pEqw"}], "types": ["point_of_interest", "establishment"], "reference": "CmRRAAAAJk5ifd8vyGmKptR7g2kvYOzlkrEFnM3dmjTYDu5ohfbZSivBsvJeVBxMfDH9ifRNc8Bml-V7Sb7Ufdnrj_TuNDRkwBdHS2F2ZPS1Oy5uU47ez1DVQ92Oyw5n3VDzNr5rEhDMtjMxQ3MqykRxv25esFUYGhSIyEX9mijvu_8IKXgtWyYbwIfD_Q", "name": "Student Conservation Association", "rating": "NA", "id": "1c5ea7722fc0d99e9f7dfca55f5d9078224d51d3", "job_title": "American-Technologies-Inc", "place_id": "ChIJQcqBXfDAQIYRErawO-goGj4", "address": "2990 Richmond Ave Suite #400, Houston, TX 77098, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-96.038102, 30.055621], "type": "Point"}, "properties": {"photos": [{"width": 984, "height": 985, "html_attributions": ["<a href=\"https://maps.google.com/maps/contrib/110279808588468038448/photos\">Peckerwood Garden Conservation Foundation</a>"], "photo_reference": "CoQBdwAAALLT7SW-3va8oXjGZTQBkXuD4yaVsxqc3_0S74aDGjsWSsEnSYzQZeNQ3ReSK3vxP3pgTyg_zHzBWUzbtQbrf5JFVax09GgQX7yQ1ZTHTtrK1Q_nsQlp-hX8TyCvFMMzHvM4cYUjOup6LZQ8tdksnr-61GV-jrTzaWaTsdhmR697EhBLqMi0-WHb3ghhl2sXZsKIGhTMwAzOhPvi7MJmfqxEE1jX0-VbOQ"}], "types": ["park", "point_of_interest", "establishment"], "reference": "CmRRAAAAevZtB1QgVctHglnusVO_6R8HRgsn_NoROA11gtOpKelth5ez5GC1Ri-WCsZnHssZpA273T6XM80Q07kM-mB1zgxUvzY7IKePt80o5C64NvJgTjCR2fNAjdP6JwkAlRS3EhBphDQ1nZZNG3BLrwl3XHSTGhQVHvratRmel7M1KKah1qhEUX108A", "name": "Peckerwood Garden Conservation Foundation", "rating": "NA", "id": "e618a4c618cd67ce4f5fdc165f640220ab3b53b2", "job_title": "American-Technologies-Inc", "place_id": "ChIJmUR7pvHKRoYRIIl0o73bPGE", "address": "20559 Fm 359 Rd, Pine Island, TX 77445, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.64386449999999, 29.7515036], "type": "Point"}, "properties": {"photos": [], "types": ["point_of_interest", "establishment"], "reference": "CmRRAAAA3or994ekZJgsXxoVacRciBUGJ8kWlG-qMQh2WeyA9c9Asi7RRW_y5mwAOYDZJXwFA93r4J-QWWf-zVcuwCU7gXgDxiA7jMa1OCKRK5fyKxhGPJMwZyMdi5edFg4_47uiEhCuyuHIiQo8iREqVmHxtXXdGhQDBHLUXAz8cSCCCF-NR019l9UfnA", "name": "H2O Conservation Technology", "rating": "NA", "id": "30c07988ef8dfc62dac712b9d587daa4a36f2539", "job_title": "American-Technologies-Inc", "place_id": "ChIJIWZRKeHKQIYRXxta3wOMGGc", "address": "1725 Hwy 6, Houston, TX 77077, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.5705632, 29.7714443], "type": "Point"}, "properties": {"photos": [{"width": 3024, "height": 4032, "html_attributions": ["<a href=\"https://maps.google.com/maps/contrib/108143329814504597326/photos\">State from Jake farm</a>"], "photo_reference": "CoQBdwAAABnUiGJAtlXIevPB9jSNdbW855URUu5kcIh7b0rdfAgmvh0-I_DxtEElByTFNXhoLI2MlIzOJ6aQhL_DdREofo1IgjixsXtRpB031DNKNwxNTAgQ5XgvFKL4RB8TOCQBTH3So2GA5RdhEzQsUge_8uWhOitTq12iFrDNbPlpeCV-EhCYRPz-li0Ds8nUiQrONHPSGhR14Nu7nkdWBnJiu6BMro61kYN0aA"}], "types": ["park", "point_of_interest", "establishment"], "reference": "CmRSAAAAD2kH9duuUOqYvIqT6MYuqAzlkAk9H9NF2lVWWFbgPHmcCHJ0reAeeBweE3sIoGCaosaL36SRCDP_CaE0nSTpPx31kBlSuHXt8EfiH67rjTyynV7AXpvHvWkbGN0mcvTFEhAc5cy_q_5N9kzKu0nVRf_YGhQk5iXnFJUMtWCoB332juOBZDXW5A", "name": "Houston Audubon Society", "rating": 5, "id": "050a5458d86bdd1cee7b09678bd6256d0a20a73e", "job_title": "American-Technologies-Inc", "place_id": "ChIJlQOxwVDbQIYR2uX_TZl0TYc", "address": "440 Wilchester Blvd, Houston, TX 77079, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.56820189999999, 29.770778], "type": "Point"}, "properties": {"photos": [{"width": 1800, "height": 1200, "html_attributions": ["<a href=\"https://maps.google.com/maps/contrib/108765250995932379967/photos\">Audubon Docent Guild</a>"], "photo_reference": "CoQBdwAAADjbGksk8MVym2SJRh0YKpbnemMC7xMpH2SQXnZq0KjMFFicjDFP2rgsJXHZ3MEkLbI14uTTwUVzWM47sXtYs6EvUe9H3oIatyMHfuwy2irsytGw5_qqSYPe8S-J-5ehlkvJmHoYXc3_iHV3tJtg2PfJK-rK28h0qg5q99eNYTooEhDKcgzXzg3L7MPqrwGRgATdGhTRzvZUpkKBK0XDh6zQxK6psq96DA"}], "types": ["park", "point_of_interest", "establishment"], "reference": "CmRSAAAAPEcV8Mgzu-_bZmTkaayEnvsZyOofdds_vI9Aqhw895nVfqRF-zoUnypj9QqxTvJlWM8z_a7YQ0IPX4pQoTiVCZaIwmncPjB_PNqbn-LRwuHRZh0xYc0mOkmNKNEw6GfwEhCOtkPJiqbRpOn5SK0Jqs9YGhTrmjBoKyXXmu_t7rfHrHejj9cdFQ", "name": "Audubon Docent Guild", "rating": 5, "id": "7ddd5daf76cc4979e2ba6b062322d1c77d5d1c07", "job_title": "American-Technologies-Inc", "place_id": "ChIJI9XyNFHbQIYRtwHb8EtTpeU", "address": "440 Wilchester Blvd, Houston, TX 77079, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.44932349999999, 29.7803218], "type": "Point"}, "properties": {"photos": [], "types": ["point_of_interest", "establishment"], "reference": "CmRSAAAAcJLCHyRFV8aJgmVerRG9Hfj8JHyudLlRvs_ebnzG9sqlRXfaT2yS4kqINadc2A_GAJw1py4iY0g-dFE3mM3Co8X69Ewhm4prAk_48JsyX9L9ox55nbJlf8YoOy9SVwAEEhAO-n1Bv2jjGPrXzQJ6Zt_qGhQGjyrgfFy1BrPOHs0v72tv4X61SQ", "name": "Coastal Conservation Association-Tx", "rating": 3, "id": "7258b034e119f31e82320bca6e72781ee9f79d75", "job_title": "Typhoon-Texas", "place_id": "ChIJcekacM_GQIYRPzL13cgQrPk", "address": "6919 Portwest Dr #100, Houston, TX 77024, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.47039, 29.655454], "type": "Point"}, "properties": {"photos": [{"width": 5312, "height": 2988, "html_attributions": ["<a href=\"https://maps.google.com/maps/contrib/101184977609161362375/photos\">aug4</a>"], "photo_reference": "CoQBdwAAAI1KQGG2PpsyM5AqQKQB4oX6k-l2rFvNVMhMHyGhtG0V8T1UeTjvziYtw6-QbwIfJMiSk1HIjLL8c5F9BqhTEXjoxUeOXg5GJh4bvy12SGHnZegNDbsIbXTGUaX4sT6eEpeI6RTdtvHfXm0oECusFok7gex301WXu5uiU98kNIocEhAvwGnE_azN4b2Hp4oQ8moQGhTlB38Pg8Uun9DkXdXHYMQhYhMZsQ"}], "types": ["park", "point_of_interest", "establishment"], "reference": "CmRRAAAA9ywMNmuxl7m7up914Cx4lnsFo2XrGr8dufBQPouLZPIYFKlrg93WYdRI-af1zgSw5dR4whSrZwvuo9WvYyvbTsEvtUYiipCSkrRtoEIqBy7eKa7rXnC9BMkcV9EwK-cpEhCqgBY7Rg7Lri_2HCzHroEBGhRrvO2dLi5we4YSoaCBYgZP5liy4w", "name": "Willow Waterhole Greenspace", "rating": 4.3, "id": "0127506e8071350c2d48f0ca56e939045297a0f4", "job_title": "Typhoon-Texas", "place_id": "ChIJR6_2zTzqQIYRsA7wExgfDWs", "address": "S Willow Dr, Houston, TX 77035, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.4003322, 29.7388505], "type": "Point"}, "properties": {"photos": [{"width": 1136, "height": 640, "html_attributions": ["<a href=\"https://maps.google.com/maps/contrib/117056878997299689379/photos\">Marisol Brown</a>"], "photo_reference": "CoQBdwAAAEw52-2fyrp28_y_WPoH4yNz561wBdLY8DBN-MrZHi_8eMpw99YIFTAUiLzFsLJBNdxUBkJGBAtoTLIxTFsUFkVt0cWN3qXsUWCgoMskr-yZg1j_tRtdSUvlPm6hi8rFHEFo8tLapMcAHpnCh7lh8B2ZrGABn5n2cvNalBMksqBmEhDYfO3t-OnAtWdEXK57_hocGhT2pKOP3srPtGiJjQMZlUwO5ZJbCA"}], "types": ["point_of_interest", "establishment"], "reference": "CmRRAAAALnPDh0SgnQYTO_CzgZes4vRp2H1gMcOMsKB_ZCsbwvTK9KfbDdd8yCqULoLjZdTpmM5peu1E7VyKKvEhMAKARh6gUSOT3ZkUUuFkvMgfHBTgauTQfQQVyZrujkcXVwHiEhCv1V9TySUd4cb9zLxwnG66GhQMFH_nQo61mDwtUUUJ0Z93LqrcRg", "name": "Masters Fine Art Conservation", "rating": 5, "id": "a462c2eef4e22ea319485ae7b84f3d20756cbdd1", "job_title": "Typhoon-Texas", "place_id": "ChIJp8u2bZvAQIYRbosnWz6cVmY", "address": "1612 W Alabama St, Houston, TX 77006, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.3876169, 29.794149], "type": "Point"}, "properties": {"photos": [], "types": ["art_gallery", "point_of_interest", "establishment"], "reference": "CmRRAAAAMLNkq8SPDc6Yi_7IltxCT7qgmfSzcEI-uLCgCXxOtuQqHYNUbsYrosaTRpicEmrfqSCs7FcPdPyGLWmNaeGGmG1w6m5hd1ZIBgLxEZR7vhvCZt23gVdDgOGtX3RwNu0tEhAecUmGaeRAkBsyESbmU-A-GhS_wDzIvYbEQm1y5k_qY7Um2LI7KQ", "name": "Whitten & Proctor Fine Art Conservation", "rating": "NA", "id": "883a8c5ef35ab28e1630235ad65a6b16506a67fa", "job_title": "Typhoon-Texas", "place_id": "ChIJ8YuXE6K4QIYRn1SF1hazFEw", "address": "1236 Studewood St, Houston, TX 77008, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.3858767, 29.7300997], "type": "Point"}, "properties": {"photos": [], "types": ["point_of_interest", "establishment"], "reference": "CmRSAAAA8By7vF8zIkBYknC37s1DX8PgAJS9adroJB3KsjfhUuE29YadHhkydIjyCokvtV6nEs2WyxpF8u9gDQFSy1ajoiRfR34GzdCQyIfQ04y21g2w6BBLQa1YA6wac9M-pjCLEhDLllORQfdXlohapnLBpiYvGhQ3uO_Wvuq_ke93x0TtFQXrp7-uXQ", "name": "St Mark Fine Arts Conservation", "rating": 5, "id": "ea2d4bac6d74716b33f456dff3aae0cc0b43cca3", "job_title": "Typhoon-Texas", "place_id": "ChIJKbDEoXm_QIYRcRFBlp0dE8A", "address": "4901 Main St, Houston, TX 77002, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.483218, 29.7482286], "type": "Point"}, "properties": {"photos": [], "types": ["point_of_interest", "establishment"], "reference": "CmRRAAAAhKuxFyrMBIKUZWbrlwyJlTmk71tXmg31ubmHWdmMkmMHmfbCq0Bhn1Qv_is_O9b1n9az5vMZaAbl-m4jNjZQ9NRbVZ4mT8aeoslybbVM-2tZKrbROs4pFveeC_-AS6E5EhCGIoNtvI-LWhLiyYLBpDNVGhTgnmGU0e-boV8IhT3g1HDr6M_GyA", "name": "The Nature Conservancy", "rating": "NA", "id": "90af6fb9fb926dde9f7103577cebc4150bbb1dec", "job_title": "Typhoon-Texas", "place_id": "ChIJq-m4EX3AQIYRJkn4Lhccp2E", "address": "1800 Augusta Dr #240, Houston, TX 77057, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.42318089999999, 29.7345943], "type": "Point"}, "properties": {"photos": [{"width": 750, "height": 437, "html_attributions": ["<a href=\"https://maps.google.com/maps/contrib/106788706324997826205/photos\">Erika</a>"], "photo_reference": "CoQBdwAAALCCl61Wkv4DWKhywN4-XhnAdm1HdgqsHLvNHskqKGEAwesRtqfAQymR25UXpTt5BMY5rZYC549ESlkk-tpZvyPpxIU9QMI8txzzIwi2JDVvmwsByfUc2WaePgXXoacoPdH6Y36QFCQJOXbQsRFIGcw0y2lgKwx6TqErs-UVr5riEhC4wCGkj84TOiKLElFZ6Cr_GhTp3CI1_ukTSUOUMYqTUPoSAlrzoA"}], "types": ["point_of_interest", "establishment"], "reference": "CmRRAAAAmJLnxw3VG-YMh0wBX7mfoASUqo6JDeDw91Xf303MU25ewvYpYiSvSg6MHamBez55QsCEUDkCN4uO66mvB4TprLmY8OX37MrDc8spCe-CHefbK1HnzVdlQR4GmayBTxXMEhBl4EYAUzKHGlTK5Njb4qrZGhRjxsAcqjLtUXZq7X5u9iqKKp9QBA", "name": "Student Conservation Association", "rating": "NA", "id": "1c5ea7722fc0d99e9f7dfca55f5d9078224d51d3", "job_title": "Typhoon-Texas", "place_id": "ChIJQcqBXfDAQIYRErawO-goGj4", "address": "2990 Richmond Ave Suite #400, Houston, TX 77098, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-96.038102, 30.055621], "type": "Point"}, "properties": {"photos": [{"width": 984, "height": 985, "html_attributions": ["<a href=\"https://maps.google.com/maps/contrib/110279808588468038448/photos\">Peckerwood Garden Conservation Foundation</a>"], "photo_reference": "CoQBdwAAALcN75mvojkuxlVbP23BDf0TX-J-FxjRR0WHUEeLykjLxAWXk6PLn--IFeBeR_6K27xFmBBhRAjdh7k1KtDgAwzp4qrRN7mBrpMSE1iOqjlM2GbN-iV6KSrmo4hQNDp6cVaEUtwC2KkSbOCuxNjg1t2K1Sw1ynKfWDaNSeFwUbgJEhCH9XUAhHU2W3gCCcnyWpGkGhSnvjtrotHT3BvJ0E5a3tP0VfXS3A"}], "types": ["park", "point_of_interest", "establishment"], "reference": "CmRRAAAAMZ3XRmQC5LdZJqQNW6vhR9qZ1dgBiHA6PmZftpSqn5lRBHXjgg_mTSiadpo2SpMuX0H-RIR5LD-dbFKkdPWxBbqMm_4Dl2-JblqQXe0NujFAh0GJn5oaMi_FOVJcLNKnEhCOppNrWbMJ1uK1Uzdj5ezKGhQQaQuCGwqODJmkb6XijkPHcTW58w", "name": "Peckerwood Garden Conservation Foundation", "rating": "NA", "id": "e618a4c618cd67ce4f5fdc165f640220ab3b53b2", "job_title": "Typhoon-Texas", "place_id": "ChIJmUR7pvHKRoYRIIl0o73bPGE", "address": "20559 Fm 359 Rd, Pine Island, TX 77445, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.64386449999999, 29.7515036], "type": "Point"}, "properties": {"photos": [], "types": ["point_of_interest", "establishment"], "reference": "CmRRAAAAM5eu259X9N0KvaekJHeF-Zo5TOjmU64001chZQbgFJ4OJyrArYSDzWAl8R_t9yHrA4xR2t0fonaGxWJcKgIh2QTb9MLZ9w-Nq4udXLd30gTKJfreVlU6sa6_i48Bzv0xEhBBncJ2pCLafLXcbJAUIGJUGhQuhbHNPPv_LFvCwardSMOZqPyGRQ", "name": "H2O Conservation Technology", "rating": "NA", "id": "30c07988ef8dfc62dac712b9d587daa4a36f2539", "job_title": "Typhoon-Texas", "place_id": "ChIJIWZRKeHKQIYRXxta3wOMGGc", "address": "1725 Hwy 6, Houston, TX 77077, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.5705632, 29.7714443], "type": "Point"}, "properties": {"photos": [{"width": 3024, "height": 4032, "html_attributions": ["<a href=\"https://maps.google.com/maps/contrib/108143329814504597326/photos\">State from Jake farm</a>"], "photo_reference": "CoQBdwAAAAOXfBBCbUv0gSFyDOwzNhOVggcicaA2eAKdYHIf8hsMj6vc_GF6TreCa35nd9KILl9128kdc3EjnGd2jhDhnE-bg9JWH3R3z66jPoR9FMdj2Zwq64v5s_FuxpOD8hHUVGdCxZD4K53f2oVMHoD7GGYY-9qUw0CVkI_pe79jm_u1EhBnxjMDG07jYOePHHws_Q47GhRL500EVhChfi8ZN9BnNpPS_JCCzQ"}], "types": ["park", "point_of_interest", "establishment"], "reference": "CmRSAAAABEoP8AHbLIgDI4qnxrElWdEfLjeKRwtppNURrmWq0ROw0NFwHM-TRudI1gkuHPDJhEzqDLV01lsGos7iGRiPWEB0cTPmz2ND43npwZ5XfaEtqq0TPsCYKAWV_1pCGT9ZEhBoId3gFL8VN71-LMzqyvkmGhTR_eKHA_Lyiqz3o4mq_Ln5ho1YPQ", "name": "Houston Audubon Society", "rating": 5, "id": "050a5458d86bdd1cee7b09678bd6256d0a20a73e", "job_title": "Typhoon-Texas", "place_id": "ChIJlQOxwVDbQIYR2uX_TZl0TYc", "address": "440 Wilchester Blvd, Houston, TX 77079, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.56820189999999, 29.770778], "type": "Point"}, "properties": {"photos": [{"width": 1800, "height": 1200, "html_attributions": ["<a href=\"https://maps.google.com/maps/contrib/108765250995932379967/photos\">Audubon Docent Guild</a>"], "photo_reference": "CoQBdwAAAA__XozlHgpSBucMi_-a28oXcA0Az86bVbeTBOyww3LVDl5_HaII0eoa0dUOWVbSVROoJq4dwh4gj6-biTrSmJRDxVPA350VqEKwAVf0R7CVNCnZugmGrKi-mN655tX1TZPQ3cJ9m5dYYNjjifCYTRmVZZpV-iM2Gd-BjSyySTCoEhDQue9P7EB-1MHh2_xtp3yFGhRUGo2t1eDkON_W6jADz_0IQS2qkA"}], "types": ["park", "point_of_interest", "establishment"], "reference": "CmRSAAAAq-efXjig1sHsrSKV5_Ti7CmV0l3FxtgTEe79rc2d6G4H-kYMkQtbI9HPM72v_8lhcmaK0pBD0RXaRnWMG8-4OrT8Owv8SIZnFeB6TVefKyLH0O3jdGENL4a68zIdJ4-lEhBugFP2dIfGewPxAbSQedlAGhTrmmWGlakHLVpBj05QDmGBjVRLBA", "name": "Audubon Docent Guild", "rating": 5, "id": "7ddd5daf76cc4979e2ba6b062322d1c77d5d1c07", "job_title": "Typhoon-Texas", "place_id": "ChIJI9XyNFHbQIYRtwHb8EtTpeU", "address": "440 Wilchester Blvd, Houston, TX 77079, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.44932349999999, 29.7803218], "type": "Point"}, "properties": {"photos": [], "types": ["point_of_interest", "establishment"], "reference": "CmRSAAAAQ3J01zsYTwJmCLDXZ5wcdvVdMza1zcV_IiGdTGzIFACGPKuRu0iqASoEteVHQhM5ldQ4BUxuPu063xKZHJosWCN4LvRoin5tm2h5nqaZyHKnt0vX7cgj_CjGpo3xt8vkEhDKCF1eds3WOMa6GjGwf0VMGhSwuM3_2RltobcYf7pBgWBsuabgVA", "name": "Coastal Conservation Association-Tx", "rating": 3, "id": "7258b034e119f31e82320bca6e72781ee9f79d75", "job_title": "Yes-Prep-Public-Schools", "place_id": "ChIJcekacM_GQIYRPzL13cgQrPk", "address": "6919 Portwest Dr #100, Houston, TX 77024, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.47039, 29.655454], "type": "Point"}, "properties": {"photos": [{"width": 5312, "height": 2988, "html_attributions": ["<a href=\"https://maps.google.com/maps/contrib/101184977609161362375/photos\">aug4</a>"], "photo_reference": "CoQBdwAAAFilTtejuLlsSctbrPEmlqayoJ00n_xOGos4yjqAEdphjiwS_oion7wjknF3pDn8_k97aYbPdAY9qnDykXWR_WwyyyLfQalNHZFksiL8a3YqVjq4iDlyVOCr8Ql7yAzrXYIdHDcjbUpddH_0sVIQhHRIhRC-7OhTX9eFGMl_ujtrEhDpsM-ziabdCODJqkUuiHQzGhRrSB9t8oTVDfP0UoKOQiL3b3v8bQ"}], "types": ["park", "point_of_interest", "establishment"], "reference": "CmRRAAAAn78hJBuqdN_reYH_xWoNzbkFDWvO5abYpeAZJPBhYrats9f6NlWKCVHDYoOYS_9MIQ9WSqFh3D-3z4Buz0jwOYW5TSnwy27g3w-r-TGWdCvTDT1oY1oyAlLm1OSQGYjzEhC8xf_7eES_7migLXEcp1HBGhQX7mWXFpsqd0hznRfDJYSMZ7K5Dw", "name": "Willow Waterhole Greenspace", "rating": 4.3, "id": "0127506e8071350c2d48f0ca56e939045297a0f4", "job_title": "Yes-Prep-Public-Schools", "place_id": "ChIJR6_2zTzqQIYRsA7wExgfDWs", "address": "S Willow Dr, Houston, TX 77035, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.4003322, 29.7388505], "type": "Point"}, "properties": {"photos": [{"width": 1136, "height": 640, "html_attributions": ["<a href=\"https://maps.google.com/maps/contrib/117056878997299689379/photos\">Marisol Brown</a>"], "photo_reference": "CoQBdwAAAPDgaj5jXaca7Qsrm5j6FuCn4imq4wIKJvTdDgycZWczDB00_vCmOObVwEOfpi8KEaZ0X02nYEtj815kvZrVFrtl-KLbOv2Esv6HNOcinM9dYWCzZHW9_PgXO_pnapXJOqaQ-bI-MefVjooV9YeJ9q-B7mdtAkQM_q8_hvqCc7ruEhDDP9BliYTTCoM-TcqY4P1XGhTrZ33lu6As1P5WPFB9MGnOHsNKsQ"}], "types": ["point_of_interest", "establishment"], "reference": "CmRRAAAAjbI3D_8aiM64IBZdIxfO9ky1n3J6F1jqyOSP5MF2NnZp3gY_aE9YTX1XJNYr6f8KaEegt44SpaKx2ue9xtSoyRpBD1AzAUDxlq1GALIRve31hHyldQWXqWZ-18Evz5KhEhBcifl6l9QdI5-wnGdVA-9RGhTlVG_L4LeDPrTlIz9tYYDqsadQwg", "name": "Masters Fine Art Conservation", "rating": 5, "id": "a462c2eef4e22ea319485ae7b84f3d20756cbdd1", "job_title": "Yes-Prep-Public-Schools", "place_id": "ChIJp8u2bZvAQIYRbosnWz6cVmY", "address": "1612 W Alabama St, Houston, TX 77006, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.3876169, 29.794149], "type": "Point"}, "properties": {"photos": [], "types": ["art_gallery", "point_of_interest", "establishment"], "reference": "CmRRAAAAqFuoi5GnVOOMB40m8ZFPgstF0SBBU7SqFY7-OQTI8h4W8NN5aBi1IrRAPO9sRmF0vA2M0-4ff_hkl8iNHLd8Q1fSam-vele15AJtFctLusTMqj6puOVbqRM-jjllSH6fEhBU6T8kMrcE7lJhWv3VJFXPGhT2OMs8TuYMaTEPejFzTJ2mgD_rxg", "name": "Whitten & Proctor Fine Art Conservation", "rating": "NA", "id": "883a8c5ef35ab28e1630235ad65a6b16506a67fa", "job_title": "Yes-Prep-Public-Schools", "place_id": "ChIJ8YuXE6K4QIYRn1SF1hazFEw", "address": "1236 Studewood St, Houston, TX 77008, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.3858767, 29.7300997], "type": "Point"}, "properties": {"photos": [], "types": ["point_of_interest", "establishment"], "reference": "CmRSAAAAgp9pWR5qM5VMWplsKEtQBT5HxyakNu0KukoTbeh5CAvseSCkxb-082gXvYqAS0-NZR_l1EK74gNFuNaEHssNF8tyon6PcRW2aZtp_sQFdaE1DZ4EnZ6VRg6WdEpOoNfyEhDHAh73KxgptLzbZa-iueHtGhQzLREFTdBkSLr7nyuKlyZhrXzCOg", "name": "St Mark Fine Arts Conservation", "rating": 5, "id": "ea2d4bac6d74716b33f456dff3aae0cc0b43cca3", "job_title": "Yes-Prep-Public-Schools", "place_id": "ChIJKbDEoXm_QIYRcRFBlp0dE8A", "address": "4901 Main St, Houston, TX 77002, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.483218, 29.7482286], "type": "Point"}, "properties": {"photos": [], "types": ["point_of_interest", "establishment"], "reference": "CmRRAAAAPxfc5lg0G9Jq9UdPAjBMWgSqjHHAp9NpVpE_DLH-W79Fb3PH56Zg5AXkT1tki6afEhZ891qyMW-LXU1YkZsPNlV84YQfNo9Z1geIOFcWOE1t9YK0Y0iqs54XK28N-s9vEhBdNPfT4oVp2YNFDIuP-ulvGhTpOMbdYoHvVQwlgEqr7OZPfrbYYg", "name": "The Nature Conservancy", "rating": "NA", "id": "90af6fb9fb926dde9f7103577cebc4150bbb1dec", "job_title": "Yes-Prep-Public-Schools", "place_id": "ChIJq-m4EX3AQIYRJkn4Lhccp2E", "address": "1800 Augusta Dr #240, Houston, TX 77057, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.42318089999999, 29.7345943], "type": "Point"}, "properties": {"photos": [{"width": 750, "height": 437, "html_attributions": ["<a href=\"https://maps.google.com/maps/contrib/106788706324997826205/photos\">Erika</a>"], "photo_reference": "CoQBdwAAAB2JDC3TpHP4Gpo3vFzpCpmjXnvad7-lMBSNpAKWxpe2Moc-lQ2lfEFUE4RguXAUQ_Cce7wx-7fowNc7ttn13o9qcKcOBkwcqwCwwkS5ktO3WNTM35EmigCTsH75FD_X3_bb50sw2W2PyUSK0QWOLxqQ2QX2N5CFNq_KAgVhHmdXEhAYWSC_zGi2RoTfWkuF7wdLGhR5TrBDuAAIFUo1yZXkYiOQ64DmgA"}], "types": ["point_of_interest", "establishment"], "reference": "CmRRAAAA1wid5-tW402RbLGYa11ICfS8jWtFKrHqvGi0n9CzmFMojrhUPs-DVi2yX7JUjcBJz_lbIhAy085AMrj7y6tjwxrm5LtGYnswqtIAOCHjilHsjbtufNySQVbWT6DlS44nEhAVQkOuaZSfi_mJ8NN-U55TGhTh687iV9IA7VxejKa7M34oL-EF1Q", "name": "Student Conservation Association", "rating": "NA", "id": "1c5ea7722fc0d99e9f7dfca55f5d9078224d51d3", "job_title": "Yes-Prep-Public-Schools", "place_id": "ChIJQcqBXfDAQIYRErawO-goGj4", "address": "2990 Richmond Ave Suite #400, Houston, TX 77098, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-96.038102, 30.055621], "type": "Point"}, "properties": {"photos": [{"width": 984, "height": 985, "html_attributions": ["<a href=\"https://maps.google.com/maps/contrib/110279808588468038448/photos\">Peckerwood Garden Conservation Foundation</a>"], "photo_reference": "CoQBdwAAAKUtsQx01HS1hgLbTi4yLptWPNmYkCe6ElyOGgoZ-GPKUZVe4khF3Ql230kvmX_eimlRBRwqwXou4EtdlG5BJpzpk8xhrAzXcG8Yhw1HyKX2GmyWCVH-RZTEZXj1-BLpbY_r4w43IGyYXXRx98vs_sP12BvD1dhS5aRVfy_i2NZiEhDeTOgMDxBlxSBpDot0yR5lGhS6LExv-QD9PzajmgS54ECRzdktog"}], "types": ["park", "point_of_interest", "establishment"], "reference": "CmRRAAAAb50K7YPu40f5adymFJJu4lCVt7lTwp-daebKAx1ZaNVEiGXn3V4ZsnQiSY3WXT1se_VyXfEkRR4fQ1AXym3uIw4kgxBEFTCiRUAJ2CfsG0L4u9RLEYv4mukPU566liuCEhB6C1mpQDqlj4PVwD17V-EiGhSEnmIUEu8vNht5cE16goRkovAL2g", "name": "Peckerwood Garden Conservation Foundation", "rating": "NA", "id": "e618a4c618cd67ce4f5fdc165f640220ab3b53b2", "job_title": "Yes-Prep-Public-Schools", "place_id": "ChIJmUR7pvHKRoYRIIl0o73bPGE", "address": "20559 Fm 359 Rd, Pine Island, TX 77445, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.64386449999999, 29.7515036], "type": "Point"}, "properties": {"photos": [], "types": ["point_of_interest", "establishment"], "reference": "CmRRAAAAsI-d8a36xE35qFimXRtry6QTDrDBKHm4XBy6c3wXLoZlPITKNE65pA7sk5lZ-w281bwV-toLoDQINj_0xR5QUibDT4flRyrQM6auwLjWl-yOezZaxsvpW7Kz_CZzL7W8EhB7qy-hBLFufsHKVJ6PbIgjGhSqPYi0SqpxbDwgFkCuUQOT1H0ZzQ", "name": "H2O Conservation Technology", "rating": "NA", "id": "30c07988ef8dfc62dac712b9d587daa4a36f2539", "job_title": "Yes-Prep-Public-Schools", "place_id": "ChIJIWZRKeHKQIYRXxta3wOMGGc", "address": "1725 Hwy 6, Houston, TX 77077, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.5705632, 29.7714443], "type": "Point"}, "properties": {"photos": [{"width": 3024, "height": 4032, "html_attributions": ["<a href=\"https://maps.google.com/maps/contrib/108143329814504597326/photos\">State from Jake farm</a>"], "photo_reference": "CoQBdwAAABmPc-jnuMS656ZMms29p7jtPrIlQQVJVuOyB3k5D4Jm_5VV2AO6aAFGvFExI-v8z2SdrG3HWVDFWNWnt-NIy5suhx9r22oBUWITfvRMmhuO3RED-h9aMZERvpfd_vQ97dJiKwE-otrqAfdIT4ZxnDVS4HLyKmsKpaMgNIU7PIgQEhAXfGM-6gX7aDtjeHGB0zHTGhQ-odzHzV-7e-G9q4TfgOqwgx0ZNg"}], "types": ["park", "point_of_interest", "establishment"], "reference": "CmRSAAAAnqoF4lyAOK69DWktWK4Iawjsyn6_qOROBRyu6whmpAv9COjWGP9xna4tCg7c8oS8txNzCs_AqYZ_40CTWS59tPwo-_Rt2id-0dyR8C3Fufp9XdxCO25jhgbFccOVWbavEhBBO-GQqJkJ98nsI1QUemW4GhRQ8QiqLPk7IgfLxqpf4-oT3VF-_A", "name": "Houston Audubon Society", "rating": 5, "id": "050a5458d86bdd1cee7b09678bd6256d0a20a73e", "job_title": "Yes-Prep-Public-Schools", "place_id": "ChIJlQOxwVDbQIYR2uX_TZl0TYc", "address": "440 Wilchester Blvd, Houston, TX 77079, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.56820189999999, 29.770778], "type": "Point"}, "properties": {"photos": [{"width": 1800, "height": 1200, "html_attributions": ["<a href=\"https://maps.google.com/maps/contrib/108765250995932379967/photos\">Audubon Docent Guild</a>"], "photo_reference": "CoQBdwAAAKKw9uX7dhq537HLqwz2VcifKOMl2yHGyeE17_LcJAdCxU8vZKLMuXQBxY1Miw8q6Yek6t7goTmTKofw04LBPDWdho0buuC0B9Z7uSVF3X9NV1Cg-ncps50yZjai-n430-YyWEQhfziFFzBYA5pegt-HK0Xwx52E8pDCje-Q6n_JEhDUH-VSEAFumsACpCJ8Wz1EGhQVTm-OeSeM98UzFCv_3y3RB6s3eQ"}], "types": ["park", "point_of_interest", "establishment"], "reference": "CmRSAAAA3bBWnvVAsqoTerRg_M5ydChhfEU3_BsGahjXcnIHE8MJg2-omsCw30R60LRjqg4d0VGT7Iwdj5N58pmAUUc6XaT1TvhzaAXiiOqpv289_Jer_9UVI024tYh21ZYapHuTEhCpLf_NF6PJDUYx5Eg4OfXeGhRhPFm0TxCDvJRGPdrf8NJoguV30g", "name": "Audubon Docent Guild", "rating": 5, "id": "7ddd5daf76cc4979e2ba6b062322d1c77d5d1c07", "job_title": "Yes-Prep-Public-Schools", "place_id": "ChIJI9XyNFHbQIYRtwHb8EtTpeU", "address": "440 Wilchester Blvd, Houston, TX 77079, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.44932349999999, 29.7803218], "type": "Point"}, "properties": {"photos": [], "types": ["point_of_interest", "establishment"], "reference": "CmRSAAAAWrJKDyf5H94Ui9O49yD-5tTbIXVJzpIFUZF_RXrR2bJ6f_VA516yYBvsCMRH3_ZvbW3YVQel-2-uLGHBj-m9b67RBfCPoerNdRsx9b8CDVvNT-5FfzI4ATvaHAZXxybGEhAIIEkL8Jsja1L-N5s0oTziGhST9CvK2dgw4rWgpftA6WIIgduS2g", "name": "Coastal Conservation Association-Tx", "rating": 3, "id": "7258b034e119f31e82320bca6e72781ee9f79d75", "job_title": "Mei-LLC", "place_id": "ChIJcekacM_GQIYRPzL13cgQrPk", "address": "6919 Portwest Dr #100, Houston, TX 77024, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.47039, 29.655454], "type": "Point"}, "properties": {"photos": [{"width": 5312, "height": 2988, "html_attributions": ["<a href=\"https://maps.google.com/maps/contrib/101184977609161362375/photos\">aug4</a>"], "photo_reference": "CoQBdwAAAH19SbxQV39_lw6yWKtwB-b4Axc1GO-lF9CRULReftQ1Day81Tj06S3vYjcPhlCT3v2Hj-spnxYtn1bwSrwNutNCZok8FtXZIiSfjAEDojt9CmneGejKCvnlmJDkj60hpErVepPsRTt16oNTa0JYyE3pNWhuHywty8xE98AzmwHfEhBj3_jSPM-89hNP6dMFBJZbGhSDikl7QTv9F8nLDraFARc8iiWcOA"}], "types": ["park", "point_of_interest", "establishment"], "reference": "CmRRAAAAsFLN99KgxTUnQxIYR7t1uVarchevXzTl-TlSO0fM9kNNMUkS7eEeq9JSqs8M_1m92ZTkOuNYgHdD19Qx1mL6-S5-PI-aXeZEkF1qiutppvoz8qNB4MPGsK-tMQe0UIEyEhCF35BZcJLlJ6lY5pB5uHZBGhTSTLnz9axAe4vlQnIpdHr88PY4zw", "name": "Willow Waterhole Greenspace", "rating": 4.3, "id": "0127506e8071350c2d48f0ca56e939045297a0f4", "job_title": "Mei-LLC", "place_id": "ChIJR6_2zTzqQIYRsA7wExgfDWs", "address": "S Willow Dr, Houston, TX 77035, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.4003322, 29.7388505], "type": "Point"}, "properties": {"photos": [{"width": 1136, "height": 640, "html_attributions": ["<a href=\"https://maps.google.com/maps/contrib/117056878997299689379/photos\">Marisol Brown</a>"], "photo_reference": "CoQBdwAAAIWGbGtnbJjhSLIj_l37A4AABQamVIBR6wG-fw-GoHASRAKB6CpMA_uOTyjFlq42sAzKRuUFmNvh0XbYzO89HpyYw_R1KfEr3VL5qcmQJegM1FsaVVq76ns0bzMhrjoRL307uQ2W0Q3nDcQTjKYAop_vz5kyoQDynn7LNBL0qq9eEhAOJB4poX4I9A-u45fo8ckYGhRUsA9iuVqPjPn-wQZ_MYndl0wx7Q"}], "types": ["point_of_interest", "establishment"], "reference": "CmRRAAAAQgQrDfeB-gU01BOoFHlerm3dEvGSJibC3mRAtXKKpfvttkMl4VIY8yiV_B_5PoA1MDdo41cNWJ-ufpClbpOsahe-uwe9iFe2kUpLbfWjBFIC0S3tHzSIqOWwDLCLG_XBEhCAtLgu9WDvBhkLXPolsSJYGhSc0Uztp08n47D8JlHakhadoiObAg", "name": "Masters Fine Art Conservation", "rating": 5, "id": "a462c2eef4e22ea319485ae7b84f3d20756cbdd1", "job_title": "Mei-LLC", "place_id": "ChIJp8u2bZvAQIYRbosnWz6cVmY", "address": "1612 W Alabama St, Houston, TX 77006, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.3876169, 29.794149], "type": "Point"}, "properties": {"photos": [], "types": ["art_gallery", "point_of_interest", "establishment"], "reference": "CmRRAAAAlkSnmhvVl3L9wXsIzbZqtnLB9b0T0x8dI6uVaTM_fvuu7_cx_i60uUJHlAEEUCTf0xW9_vURY9UzqJR_SggIfVI7EXJ3B_a8TVkhv3n1mu9noddvr66A46U1X05CtitaEhDKbuWGrxK8TEcFeSUxxeZBGhSchkiHs0avxCXfxbtAnaNgdmElXQ", "name": "Whitten & Proctor Fine Art Conservation", "rating": "NA", "id": "883a8c5ef35ab28e1630235ad65a6b16506a67fa", "job_title": "Mei-LLC", "place_id": "ChIJ8YuXE6K4QIYRn1SF1hazFEw", "address": "1236 Studewood St, Houston, TX 77008, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.3858767, 29.7300997], "type": "Point"}, "properties": {"photos": [], "types": ["point_of_interest", "establishment"], "reference": "CmRSAAAA0Kb0hCAKKQbWaH-CuvOXIXWmSHgQk7l2ASYx-gbQrpps6gp5nVDnAQMtNibiEqvtjPPG-qQVksQjBbXfQtJjhnKVI7_05KK6Abk9pQsm9H3Zi3WHpPJGEpouNxEZIDBuEhDCcqosdEycsz3VbVxOiZ6KGhT83UAz-1ss0w1kb8o-5buAYKUSdQ", "name": "St Mark Fine Arts Conservation", "rating": 5, "id": "ea2d4bac6d74716b33f456dff3aae0cc0b43cca3", "job_title": "Mei-LLC", "place_id": "ChIJKbDEoXm_QIYRcRFBlp0dE8A", "address": "4901 Main St, Houston, TX 77002, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.483218, 29.7482286], "type": "Point"}, "properties": {"photos": [], "types": ["point_of_interest", "establishment"], "reference": "CmRRAAAAc-yT5TWB7daoRaso-H2O5XcuqRYxS0B1e00ozPD1mQA2unMoCeoetq4K5Xyogipu5lStS11qOWeQUUUal0AyoYfVNPEQK2JiJdQ0eITW4UfRhfyh5dmC3b4RFx4XXemSEhAnkJJI7Akkpab4xqrpgt8EGhTc-a9Lbtbjbef0QnlqGb0g30Hp_Q", "name": "The Nature Conservancy", "rating": "NA", "id": "90af6fb9fb926dde9f7103577cebc4150bbb1dec", "job_title": "Mei-LLC", "place_id": "ChIJq-m4EX3AQIYRJkn4Lhccp2E", "address": "1800 Augusta Dr #240, Houston, TX 77057, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.42318089999999, 29.7345943], "type": "Point"}, "properties": {"photos": [{"width": 750, "height": 437, "html_attributions": ["<a href=\"https://maps.google.com/maps/contrib/106788706324997826205/photos\">Erika</a>"], "photo_reference": "CoQBdwAAAGXP66oe56Ge2cYW8LG3MgS2sW6Wi3Fz3hNzjOJ8oUyaVQC-PPFfpuYJCsXIaHntgCwuhsDy-LyZfY32bQCQytbEvypkgnuH3vcv0bk_IDZ92m9wRM3aHo3C8YmDZUZ9rQ0nVfLJktVRjpFxP_KyDkJaqFJP3mwPZFxQFhg2GWDhEhAh2q2tr7GlKHBdtG9IGtOvGhQEBwGvuPS4pfikaFrovVJNv6_1cA"}], "types": ["point_of_interest", "establishment"], "reference": "CmRRAAAAVWKGUHTAhjw82w5Zz93TyB5EsnpI8K20sB42EStO5-ztypFfNw_RgE4Ke7J8wsOorbXA9juGviw_HUcjPQZHZz_VQF7-sHq7NeVI6Ks3zvOWxcwka4o3LpiZXKyx7Mz4EhA5jvg_X715b_c25RVrP4tTGhQnJ-9_QJqvbJETgGZTzFM4yObEXA", "name": "Student Conservation Association", "rating": "NA", "id": "1c5ea7722fc0d99e9f7dfca55f5d9078224d51d3", "job_title": "Mei-LLC", "place_id": "ChIJQcqBXfDAQIYRErawO-goGj4", "address": "2990 Richmond Ave Suite #400, Houston, TX 77098, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-96.038102, 30.055621], "type": "Point"}, "properties": {"photos": [{"width": 984, "height": 985, "html_attributions": ["<a href=\"https://maps.google.com/maps/contrib/110279808588468038448/photos\">Peckerwood Garden Conservation Foundation</a>"], "photo_reference": "CoQBdwAAAII71txVh_8_Bu_VEfsRRc44Nk6XI62TXnPs6XZ6J5YaP1FYOcYQkbW74YyOax2iS_f1xtvrEc7icfs4yZcuXyF-37ghvGVzxRMDY1IMaffpaGiRSJoy-gfER2s4Dv5n-x17Tnq4hlrAgh5gKFaJ3FoNqRbvX_kWMjOf0c_YKE-LEhBWBwFmbjPzq0_7iLMvWgJ_GhRYDXZZPGdvlMmScgFCbYDk550yKQ"}], "types": ["park", "point_of_interest", "establishment"], "reference": "CmRRAAAAoc6KnS7APkzGYMHKq7CyPus_BUdh5Us_AypMUw8UckP9rGDKOAJr_055Y2o1CrFXWTdcMHxl9L8fbQbvu4NYOejrtki87y3c4PAvq7c_XtWvhXqgVCqI9T3RLMPsLqjoEhDPiYjiDTjyNYGFxdoX-e3pGhTHaF006jHCRIBZZ57QNpmIjUcaFg", "name": "Peckerwood Garden Conservation Foundation", "rating": "NA", "id": "e618a4c618cd67ce4f5fdc165f640220ab3b53b2", "job_title": "Mei-LLC", "place_id": "ChIJmUR7pvHKRoYRIIl0o73bPGE", "address": "20559 Fm 359 Rd, Pine Island, TX 77445, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.64386449999999, 29.7515036], "type": "Point"}, "properties": {"photos": [], "types": ["point_of_interest", "establishment"], "reference": "CmRRAAAAamtA9hG8GrFxQGUHxg2-vKbfqfg5Q4hyFaqj5VbptFyJOWEUHQ-2Q8_nkp1Kl2XMWQn2Z1IpiLAKa8QIO5WsJ4Qjobb0mx4pY9v1ykg7wAzFx4krmrAC_RGAT0lA6-tLEhChhpC7HRvt7_AU363mG9wuGhRnvueS54N7bNGcDZfoCAMJpGkZ7g", "name": "H2O Conservation Technology", "rating": "NA", "id": "30c07988ef8dfc62dac712b9d587daa4a36f2539", "job_title": "Mei-LLC", "place_id": "ChIJIWZRKeHKQIYRXxta3wOMGGc", "address": "1725 Hwy 6, Houston, TX 77077, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.5705632, 29.7714443], "type": "Point"}, "properties": {"photos": [{"width": 3024, "height": 4032, "html_attributions": ["<a href=\"https://maps.google.com/maps/contrib/108143329814504597326/photos\">State from Jake farm</a>"], "photo_reference": "CoQBdwAAAG2y3HeROa9T1598pr60sFzwlnAOqFZ9eikIYjBUglvwqn3po8t4U-vKt2WPBCsa-Gsxpd6RdXr3Q0lWKUd7wGY7Z0iYOyd3DuObRfU5jBeteN6K1sfF0IfaBSRghAlfXlkSG7syGZm1clVGvfEU-IdtXrCUAHMFaBbNoZgkQNb6EhBxMw6YF5UnZH_pdfLjTk_fGhQL0Q3tSygRbro4KnGPWynEzJHZOA"}], "types": ["park", "point_of_interest", "establishment"], "reference": "CmRSAAAAQj3cCi5pt2KNnxbQYSAW4Bd_rJ913BPb21A9mzTL3ganuUT0NA0Ed_xRud3H31VSZFzlThJ9KP6IRjlr-7H5voGvnEEED215dcIJtycdN3MkNkDyM-QS-tWoWlyXY1PUEhAvCcTWze5_VamifMA-QbU-GhSt4ktnMPhFK0rV-Bt03PMdMx-K5g", "name": "Houston Audubon Society", "rating": 5, "id": "050a5458d86bdd1cee7b09678bd6256d0a20a73e", "job_title": "Mei-LLC", "place_id": "ChIJlQOxwVDbQIYR2uX_TZl0TYc", "address": "440 Wilchester Blvd, Houston, TX 77079, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.56820189999999, 29.770778], "type": "Point"}, "properties": {"photos": [{"width": 1800, "height": 1200, "html_attributions": ["<a href=\"https://maps.google.com/maps/contrib/108765250995932379967/photos\">Audubon Docent Guild</a>"], "photo_reference": "CoQBdwAAAJQnvonsrk-YGYpoQ4H6CZOTfzCxEiGWyEc8LCuK_InW-eC3Za66sDxZm_xynVjCpnVVcF4kK_3RZp5S-D4kjpn99rldKXv_M0yFKkFg2A7WxvkdcVQ-KPHZqq86FcdZyzUoZL6io6zrZE1205SHOUJzDS_9HFREcMNqnhvIDpCKEhAMg4xTaERJ0c7humj9FkpAGhSR1KuWMvmjPQPrx9QS71OcFng5xw"}], "types": ["park", "point_of_interest", "establishment"], "reference": "CmRSAAAAxgFeGrUoJFCIgItQjKXKB_mFp7Sx9GhpHnNLayepJ5anFI7kPn7llklGsmdvNJGf8Uw4opfl2F2RxOYMErPggV6ZXgs1VODbY_cDm4XyHdkXLO65mmmdtbSKVVD1ekEjEhBiPXx3clHf_2Q9u8ZntusEGhQOeZqK-nWJIt9ddWRAL-DjgKnFoQ", "name": "Audubon Docent Guild", "rating": 5, "id": "7ddd5daf76cc4979e2ba6b062322d1c77d5d1c07", "job_title": "Mei-LLC", "place_id": "ChIJI9XyNFHbQIYRtwHb8EtTpeU", "address": "440 Wilchester Blvd, Houston, TX 77079, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.44932349999999, 29.7803218], "type": "Point"}, "properties": {"photos": [], "types": ["point_of_interest", "establishment"], "reference": "CmRSAAAA4Lv_h6gQktwhYPvZ5pBJxzqKStAg0QpvbbuEgVrm2ZmzeGzDifQ5NhCOEELRMQeYCcn0ByXgg0YG5m03Yve9qEgYlqtkzkuAPRqpj0BKAtlP0GjMywt3-NVuNtSXAIYfEhBQUk7SXWiah2WMLqDQEulIGhTwbSq7pp7jQvH0O3fd31qpZfLHRQ", "name": "Coastal Conservation Association-Tx", "rating": 3, "id": "7258b034e119f31e82320bca6e72781ee9f79d75", "job_title": "AECOM", "place_id": "ChIJcekacM_GQIYRPzL13cgQrPk", "address": "6919 Portwest Dr #100, Houston, TX 77024, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.47039, 29.655454], "type": "Point"}, "properties": {"photos": [{"width": 5312, "height": 2988, "html_attributions": ["<a href=\"https://maps.google.com/maps/contrib/101184977609161362375/photos\">aug4</a>"], "photo_reference": "CoQBdwAAAAafxCv_YnFfKwlK1lc6uLcbjCTw5TgzjpwesxypStZfdQpIs2JacGImXShT6bz1k1Slq-3lNIo1zu1DS-ghHqjkSHDUTyD469ZofFh14qVDX4dlDc-cIPjIxPABjrkeUG6hXXQ5en7TkyG2S7HHxfSXtg687FCZ32LbmDGASpfMEhD5HyC1T9ju1xrFkDRhTtueGhQ2YNHmLTpqQfJc2SAcC_WxPmCDQA"}], "types": ["park", "point_of_interest", "establishment"], "reference": "CmRRAAAALQ2KMRN6-HIJBn3h6z3MwQziwXeJf3o2tjSYawsC-2om-z8Kcl9uwyaFbZ2GgYDX4vxhuCQl94Uz3-Lt_STAFI8Scb0nayFaBc2Pt0fmxrE-aE-b_MJS-TmyNlcFO8PQEhBjjFVBfsfUzX8atjuc99sPGhTH1kwY-sAUl0hgVIsJ0zrT6xxyvw", "name": "Willow Waterhole Greenspace", "rating": 4.3, "id": "0127506e8071350c2d48f0ca56e939045297a0f4", "job_title": "AECOM", "place_id": "ChIJR6_2zTzqQIYRsA7wExgfDWs", "address": "S Willow Dr, Houston, TX 77035, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.4003322, 29.7388505], "type": "Point"}, "properties": {"photos": [{"width": 1136, "height": 640, "html_attributions": ["<a href=\"https://maps.google.com/maps/contrib/117056878997299689379/photos\">Marisol Brown</a>"], "photo_reference": "CoQBdwAAAMIh_Wea8Cx8pWzABNCVXubCwBvx93Dd1YOvAbrT9O7lNKUlC02ZC9Rwob0MAdZKe5vjpWxL08vsCO9nvxz7DBKWke1lmuCbU3thDE48vk8aab1WAewKeTJsDb2CTpB0UiAbS6hi8aPn9XApUy-vbjugzibuxU_e_iNEo_lIYq42EhAww2WV25jAFuyw9JiRHEW1GhQEbiluopGFE2mNuEMzkbNRngbHLA"}], "types": ["point_of_interest", "establishment"], "reference": "CmRRAAAAq1j83T1ZI7cihTiuIK4vdiRuLkenKf-6twdkDfEg3L9XpPbFeBP74e4o8YxL9PhHM3m7GXpoVMua2onG4okoy6H2VAlTfFUgQSdvLFVa0AwdRexxWZOH2Up3YOW1XEi4EhADdXcanz4neg7zmWd_3suQGhQAEPqOzklHVI8mk1bwa2UXuSZcRg", "name": "Masters Fine Art Conservation", "rating": 5, "id": "a462c2eef4e22ea319485ae7b84f3d20756cbdd1", "job_title": "AECOM", "place_id": "ChIJp8u2bZvAQIYRbosnWz6cVmY", "address": "1612 W Alabama St, Houston, TX 77006, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.3876169, 29.794149], "type": "Point"}, "properties": {"photos": [], "types": ["art_gallery", "point_of_interest", "establishment"], "reference": "CmRRAAAAsqcUDBTUbYWX8upXNL2EEfd_cWLWFYu40g0d2IU4D-8wDm-arQl0jB6o1BnHpKt0jxn2ZDoysmTKRM4zOwNKbUn1XPjpOCtda2PWH4ft4FYK_lZMWME_KSFysVPNTXoqEhBx8TxNIunK-Dtv9aMe_fUYGhQA-NZeOk1kLy85NPY8dehjCyFOmA", "name": "Whitten & Proctor Fine Art Conservation", "rating": "NA", "id": "883a8c5ef35ab28e1630235ad65a6b16506a67fa", "job_title": "AECOM", "place_id": "ChIJ8YuXE6K4QIYRn1SF1hazFEw", "address": "1236 Studewood St, Houston, TX 77008, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.3858767, 29.7300997], "type": "Point"}, "properties": {"photos": [], "types": ["point_of_interest", "establishment"], "reference": "CmRSAAAAwe1BPBIkfUljlD1CzPYCZ5669FilwZCSYTauDKVby1z29TpEv9SCIBZzVWF0oBPveItI_e8EdA6JrpXJMMnoP_pGelJTiyPWU5x2NvAYrVPDFHaE6_HofFGB-8DSPR-OEhBiUzELIi5_ZSRozKRwgXwUGhQoOUOnKfZ4LUhD9uqX1cT5oWEBPw", "name": "St Mark Fine Arts Conservation", "rating": 5, "id": "ea2d4bac6d74716b33f456dff3aae0cc0b43cca3", "job_title": "AECOM", "place_id": "ChIJKbDEoXm_QIYRcRFBlp0dE8A", "address": "4901 Main St, Houston, TX 77002, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.483218, 29.7482286], "type": "Point"}, "properties": {"photos": [], "types": ["point_of_interest", "establishment"], "reference": "CmRRAAAA62x8Zm5ZU26qReb_I_Wn1BEpX8FcLcPYSyyPqbZ9ImQXpCHryH3LHf1U74QSBu_ser2ghxEw9zH37ygM4T1TQ-Wfm6YHx-6GnkKhF4eFWVsgXMKXjTaThdnmaShQ6in1EhB11TqtaY2oHHxWy6SbPgTmGhSv8B5CwkJi4b4yToNKJ2DMdDrfig", "name": "The Nature Conservancy", "rating": "NA", "id": "90af6fb9fb926dde9f7103577cebc4150bbb1dec", "job_title": "AECOM", "place_id": "ChIJq-m4EX3AQIYRJkn4Lhccp2E", "address": "1800 Augusta Dr #240, Houston, TX 77057, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.42318089999999, 29.7345943], "type": "Point"}, "properties": {"photos": [{"width": 750, "height": 437, "html_attributions": ["<a href=\"https://maps.google.com/maps/contrib/106788706324997826205/photos\">Erika</a>"], "photo_reference": "CoQBdwAAAJja4oga1XXTbVHkLlrSVCEF7Rip43rTPyDrvfo_Y6dEYK6hKd_0SjzZ3ZxnOOnM52C59odo5lXpy4FluGa2tVS_94Uk4BaMQaxY-Rz-1mswuqJo-ogeqpf6uy4BZTjavxNxAP2CsIKHC7afMb62iNxConoRTacktbcKtwY94msAEhDgHiE9JY7zPfcdGWXZTPQ9GhQV46QiY_HX-BTbbfjyjS_73SkxTw"}], "types": ["point_of_interest", "establishment"], "reference": "CmRRAAAA58JivtA7Pugccpi5reygB6e7Fdexwhs5fkfQ5wZ6sHjk6m4NvnWckYfgV8n5twivPDsahcYxU23EAhDUQJsBnB1hRIJkXfzcwZGzrNUHyfU_8M4ado0yTQcYXYhmE0EdEhBJ1L4xpj5mARcGO6-yThFgGhRqFxSs4YdZzCVaqojWFL76D9-8WA", "name": "Student Conservation Association", "rating": "NA", "id": "1c5ea7722fc0d99e9f7dfca55f5d9078224d51d3", "job_title": "AECOM", "place_id": "ChIJQcqBXfDAQIYRErawO-goGj4", "address": "2990 Richmond Ave Suite #400, Houston, TX 77098, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-96.038102, 30.055621], "type": "Point"}, "properties": {"photos": [{"width": 984, "height": 985, "html_attributions": ["<a href=\"https://maps.google.com/maps/contrib/110279808588468038448/photos\">Peckerwood Garden Conservation Foundation</a>"], "photo_reference": "CoQBdwAAAFeo-Mz0s8OU18TSQhpYnYLCCN24QJ-9bmGr_JkW2Ob24GffSFZdyJe4wja3blUXFVPRD5iWExqkpPkBE-J103yrp9VZX6K9JT1CyNftGtEc5aSxZFUVKNNv8_O83OAvN2l28lUlls9wXZBqfBg1JbFhGMY5mBqHTJL3KAbchmR6EhBVZdqyPJI1d5VCXxPNRbrKGhSaZVOlTU_sp1mCu2uLTQowyEdl2Q"}], "types": ["park", "point_of_interest", "establishment"], "reference": "CmRRAAAAoszCzGKlOytAp4EnIUuWhMohTu2_19AORzQnnj7Oi21DRA_SxOSClBBKBgtKJNNdWRZf6sVK-VYPR1ZNzfLZb3m3P9h1VLqnJsSafGVeWEBkP5jjfQpvQnEnNkOQHGAVEhBC6yO2u8Knj7LdND5P4AbQGhTi5FqhqpBrtd0RKWC507HKJ8PR8g", "name": "Peckerwood Garden Conservation Foundation", "rating": "NA", "id": "e618a4c618cd67ce4f5fdc165f640220ab3b53b2", "job_title": "AECOM", "place_id": "ChIJmUR7pvHKRoYRIIl0o73bPGE", "address": "20559 Fm 359 Rd, Pine Island, TX 77445, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.64386449999999, 29.7515036], "type": "Point"}, "properties": {"photos": [], "types": ["point_of_interest", "establishment"], "reference": "CmRRAAAAPLz2TlD4mt7wN0rRV32PRy9Q7_nwn9XYFCt5qK8m__kQpESHkZ1lB8YcI35Wy_S_X75pt2PyMOTl2wCsG-dc7YHmO1Xac0nfleF7tBUCJ-fvxtBRzC0iro5X8BJDdO9gEhBxlWgFA9PR7wr5oymnObZ3GhTNqrBPYTMOzr_6Vr32cHkIf1IvVA", "name": "H2O Conservation Technology", "rating": "NA", "id": "30c07988ef8dfc62dac712b9d587daa4a36f2539", "job_title": "AECOM", "place_id": "ChIJIWZRKeHKQIYRXxta3wOMGGc", "address": "1725 Hwy 6, Houston, TX 77077, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.5705632, 29.7714443], "type": "Point"}, "properties": {"photos": [{"width": 3024, "height": 4032, "html_attributions": ["<a href=\"https://maps.google.com/maps/contrib/108143329814504597326/photos\">State from Jake farm</a>"], "photo_reference": "CoQBdwAAAOBC2oiT3rMLB7C6_cFEr6dw7tKKFDsDNPdXROGGk4OrotRmGmYzbID7Ukqnd9Tp55WjvxLpN6ZOZVaEFqJv8EPMA_srMmkcuQIeFYGtGE48hB1VpkL0oMPnMHG_X71qwYi_aWDnWpjAQ1ILvU0peXsadX6p3LJOMP5-ENdhL9TZEhA5qD27hjdDBaQ1FzAFQp0xGhTNuizozLzT5LwwUhVtC7giON6BuQ"}], "types": ["park", "point_of_interest", "establishment"], "reference": "CmRSAAAAqdaPxqSN6UJzEQJvWE2UBgDugDp7kZ9Ldd6MMSjsg-6QVQOpESzEwYD2bYA5s2dkhgCLcMNpMICkq5PxzyqDF0-iobtAJCCz_c8p8PP1SbJ21PHBvZvbjqAxTYZNfHYVEhC120RJXUZ7NtxEDyWk_Z3cGhQb2Wgp5J1ERNlvCt4am9txMM6KHg", "name": "Houston Audubon Society", "rating": 5, "id": "050a5458d86bdd1cee7b09678bd6256d0a20a73e", "job_title": "AECOM", "place_id": "ChIJlQOxwVDbQIYR2uX_TZl0TYc", "address": "440 Wilchester Blvd, Houston, TX 77079, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.56820189999999, 29.770778], "type": "Point"}, "properties": {"photos": [{"width": 1800, "height": 1200, "html_attributions": ["<a href=\"https://maps.google.com/maps/contrib/108765250995932379967/photos\">Audubon Docent Guild</a>"], "photo_reference": "CoQBdwAAAF5aUTLpLCo029ifYevckkIDrAr0tviTOX27VBRL57OWGAlC093Y9lLBxSX7K7hCISnf3FhxVa3YJcJhupGx5Y--lX78DPry-zvVAEjwdEpOBZOazi03zKbtUIw5tdJB-Jgbxk4W0YDXtC48aynmgzYqt63XZQjcqGMvE0m9UOzYEhCmUJVBUOzJ1QrylyyTXyE9GhSK-lA71DxmzeiOR1ySwB-jvE8N9g"}], "types": ["park", "point_of_interest", "establishment"], "reference": "CmRSAAAAlBjAu_FkLicISF4-ny7XxoSoQOYJxLzUrpRGUafOIryrA3_9U0TorHMRwn8S7PMNhOewlKhLqnZPcXjaOPxc2gR0LGF4McrAXUO5BHLKLIkfK-QBPV3HGyVDNYkVKW_4EhAw69mV9gHV6UaA0jqX98HNGhTbGKBP8epUG6xtDF4yVWEhnhTbkw", "name": "Audubon Docent Guild", "rating": 5, "id": "7ddd5daf76cc4979e2ba6b062322d1c77d5d1c07", "job_title": "AECOM", "place_id": "ChIJI9XyNFHbQIYRtwHb8EtTpeU", "address": "440 Wilchester Blvd, Houston, TX 77079, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.44932349999999, 29.7803218], "type": "Point"}, "properties": {"photos": [], "types": ["point_of_interest", "establishment"], "reference": "CmRSAAAAzaDGq0uTTR8-muFD34zfPnksLBdoWWHZ7I7C3Q8AT35zT0KRE4WdUM7owi00QsyO_9k0sIf0VICrcmJdg8Cd9gW16YxYorwX2iPoVI32Iibbtjb0zRVAI-kfPArfMZfWEhAO1oN1WWhIP28YgL1MvljbGhR3l67mwfZYAQ592sgiq7GloUqL_w", "name": "Coastal Conservation Association-Tx", "rating": 3, "id": "7258b034e119f31e82320bca6e72781ee9f79d75", "job_title": "Baylor-College-of-Medicine", "place_id": "ChIJcekacM_GQIYRPzL13cgQrPk", "address": "6919 Portwest Dr #100, Houston, TX 77024, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.47039, 29.655454], "type": "Point"}, "properties": {"photos": [{"width": 5312, "height": 2988, "html_attributions": ["<a href=\"https://maps.google.com/maps/contrib/101184977609161362375/photos\">aug4</a>"], "photo_reference": "CoQBdwAAAON63tIIbyYq7I9p1U0de3ZGG2TjNsjiS3ECeqvsJOZl3rjRp2mHGtms8ikUdjtjn4aS3H5pH89lSsFbBzY_tFG8wzX1k4WSqXm0vDymsTPavdab9aCUkfZaotLlMWu_zCDVJGw9v4rmE38gQnMCL0lIZTQPpRfXK0MASu1qVMo9EhBv9EnHJ1_HOFaeQfqe9ffJGhR1HjINHkZsFFPj_ikSQDzMfs2XxA"}], "types": ["park", "point_of_interest", "establishment"], "reference": "CmRRAAAAxVjgynMS6yzOPkQ_TkXUAQShSJK-U9ZgfW9wO9BcCJoXlx4rfJK698m569If9AVY4kmE408GWu8a6u43bPFr7YYVQguPBRtOUVUuhmWsH2IZsw9ItIKteQ4sG8H0WxMdEhBqhSB8yJTgZzbYzMlRsnImGhTxqbCpLzk7ollSibmCCEfG4UOxaA", "name": "Willow Waterhole Greenspace", "rating": 4.3, "id": "0127506e8071350c2d48f0ca56e939045297a0f4", "job_title": "Baylor-College-of-Medicine", "place_id": "ChIJR6_2zTzqQIYRsA7wExgfDWs", "address": "S Willow Dr, Houston, TX 77035, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.4003322, 29.7388505], "type": "Point"}, "properties": {"photos": [{"width": 1136, "height": 640, "html_attributions": ["<a href=\"https://maps.google.com/maps/contrib/117056878997299689379/photos\">Marisol Brown</a>"], "photo_reference": "CoQBdwAAACQJcjgKU6fO7VaLQbGJTLMFGqh5nps4MY0WwPbe3dCvxhXFURbixWYyKgcerge_5Y1vU5RH5fJQfhRnmZWZxjEkGof5DcGAgiyiCBDeNvo_oZu8wxUgkE9yhQfnoUjxO7XR9mmLC9LFB8GtL_NzpX9c9owS4CdmU_MLii-nYnMkEhDp6qDjO5SzT-qlFZ4AHTEbGhRYIqT0YXw1AVU_vU2Pm2mLDkjQSA"}], "types": ["point_of_interest", "establishment"], "reference": "CmRRAAAAT6Sa9-TFDvpp75BS7nmHvF1VcJSD5Y5RA1WIqZz01qxShwAybGC7cCl8ayjfm85ZAROGBrjhsurqVFF_Q3SuNkMZDp5jMymGVwAA72rK-XeJv5YtiBteVax7m4r_139DEhDgbFHfc5qniPGqG3h6ogJuGhSz1Ys4SR-8Z7AhbgpO2glbQwhWQQ", "name": "Masters Fine Art Conservation", "rating": 5, "id": "a462c2eef4e22ea319485ae7b84f3d20756cbdd1", "job_title": "Baylor-College-of-Medicine", "place_id": "ChIJp8u2bZvAQIYRbosnWz6cVmY", "address": "1612 W Alabama St, Houston, TX 77006, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.3876169, 29.794149], "type": "Point"}, "properties": {"photos": [], "types": ["art_gallery", "point_of_interest", "establishment"], "reference": "CmRRAAAAXHxJ-hV22Q8OMP0-Oj9pQJzVAmXQahIbxZlr4CSlOGEgh1modCr7kFgGk-61FAdZ2YwxVxxdPxs9eEo1U-FGc0mMhQfe2iUB-vT0RjUQf-MtgsPInC8y0sIsb1kCqS8oEhBYzq3TAimXX-jdgxR5rq7qGhRWuRiCpAnaReduU-u0zqbTQ7nb9Q", "name": "Whitten & Proctor Fine Art Conservation", "rating": "NA", "id": "883a8c5ef35ab28e1630235ad65a6b16506a67fa", "job_title": "Baylor-College-of-Medicine", "place_id": "ChIJ8YuXE6K4QIYRn1SF1hazFEw", "address": "1236 Studewood St, Houston, TX 77008, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.3858767, 29.7300997], "type": "Point"}, "properties": {"photos": [], "types": ["point_of_interest", "establishment"], "reference": "CmRSAAAA0pEVPFGyeZiHtg9vy32xn_322f2eSsvBvLb1SUgf1EpTTOK86aQMXlf5Ca223tDy17_Erkrnebl5gllLZWh3iCkBclP0pYPghZqBBscCHURNfdmYCd_HNh3OR-tF2PnaEhCpEeiaxkWlyjUlAOzXwv2_GhRsKLR1BPc4gO3SiEQySJapfKOpPg", "name": "St Mark Fine Arts Conservation", "rating": 5, "id": "ea2d4bac6d74716b33f456dff3aae0cc0b43cca3", "job_title": "Baylor-College-of-Medicine", "place_id": "ChIJKbDEoXm_QIYRcRFBlp0dE8A", "address": "4901 Main St, Houston, TX 77002, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.483218, 29.7482286], "type": "Point"}, "properties": {"photos": [], "types": ["point_of_interest", "establishment"], "reference": "CmRRAAAAeZm3ktRxGb47lyGFDbdtOqu4DNKVBVYeeNOiGcfdVoU6vNGQWfCMKvYMpCdv71aLZMe_pB9gj1lkti4dwtE-ZjxvZnCTpu1wV_1CJWmWfGIDgvaupKNQHQPNqdRX1hD8EhBSdKb7Na87jp6QdG1pVxinGhRT0ChCU0dA_Jd6gK2bUqNdtcbMwQ", "name": "The Nature Conservancy", "rating": "NA", "id": "90af6fb9fb926dde9f7103577cebc4150bbb1dec", "job_title": "Baylor-College-of-Medicine", "place_id": "ChIJq-m4EX3AQIYRJkn4Lhccp2E", "address": "1800 Augusta Dr #240, Houston, TX 77057, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.42318089999999, 29.7345943], "type": "Point"}, "properties": {"photos": [{"width": 750, "height": 437, "html_attributions": ["<a href=\"https://maps.google.com/maps/contrib/106788706324997826205/photos\">Erika</a>"], "photo_reference": "CoQBdwAAANRWVVrcJlr4tOIIVxKSWVHj6Lt2jWuqoSQAmMmvzqqkxhp6LCDyT891wEqOqCCBXgUVjB8kdoehuIGnYZ9yOOClIWuX2yyvybvIxrgKY8Ju3d1aTIGFiSY_Hx9gBckIrIBKcUWQukpLmk1d9OrmmWlOlRPdg5Z1GYrZceFmc-eUEhBj11QbR-AZ0fGhDTdrBFVqGhTAhUgPT0YoWWCAc-Sd9hsNZJeqPQ"}], "types": ["point_of_interest", "establishment"], "reference": "CmRRAAAAjgTbGQUYEZbLJDI35uQ7juCeTd09z-uMw0sSHpmanlv4NMNft09LTDNnLXa1fI9rn4sQfiCwcroIU1Dvbd5RqJ6DqgisGFyNuCSMIhWwL03Tn8R2FIouZ2T1zzIrGtThEhBixiqN1HghLAEIKB6DfcaEGhT9yXYKFV1UgonFJ5d48xAJgAvlIQ", "name": "Student Conservation Association", "rating": "NA", "id": "1c5ea7722fc0d99e9f7dfca55f5d9078224d51d3", "job_title": "Baylor-College-of-Medicine", "place_id": "ChIJQcqBXfDAQIYRErawO-goGj4", "address": "2990 Richmond Ave Suite #400, Houston, TX 77098, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-96.038102, 30.055621], "type": "Point"}, "properties": {"photos": [{"width": 984, "height": 985, "html_attributions": ["<a href=\"https://maps.google.com/maps/contrib/110279808588468038448/photos\">Peckerwood Garden Conservation Foundation</a>"], "photo_reference": "CoQBdwAAAPExi6zMRz508Foz0OUSlKSglFjsWII9HPbqYcsJNtd3fk8XR6I1XJDMZHazPHAB4DtOy-PgbFu-ApnPCw5Ljv3VSmtOcWfOG39k-YYX1zOoAFMQWVAfhR9cnVgb7Egk4d0N3c4Psm3w5rPV5myYjm5P8hnMyQbME919aP6JTMtQEhAZ8ewEuw3RQ9EY3S3tVmnvGhSycckpdpHGoQtCoOfBoFWw-gkHMg"}], "types": ["park", "point_of_interest", "establishment"], "reference": "CmRRAAAAlwM-CYRX0o9W9j37upKTDlfuaXm02qZYveteAoETwVOSw6-nCiuP55FMpP5VTRFtSII_fyemMHqamjHhTGZ-nJ6vVnb2aqzuw6Xlf2BxcfYMS0tP-bp9-_VwbmjTYq5nEhC9iAwD1Y6b0X4WGefOqeLRGhSz32mHcCKZit9ZCljD9zSmvV8pgA", "name": "Peckerwood Garden Conservation Foundation", "rating": "NA", "id": "e618a4c618cd67ce4f5fdc165f640220ab3b53b2", "job_title": "Baylor-College-of-Medicine", "place_id": "ChIJmUR7pvHKRoYRIIl0o73bPGE", "address": "20559 Fm 359 Rd, Pine Island, TX 77445, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.64386449999999, 29.7515036], "type": "Point"}, "properties": {"photos": [], "types": ["point_of_interest", "establishment"], "reference": "CmRRAAAAqYFEuDUFvb9Q-Z8_1fAmP-cXu9H-V-i1qSMeELPrVDuwXa-JXKSNBURU5F6ZlaCXFlqd7HfCFtx0gPG0wshx7fsJkVnHfrWk_KmfcaNrQ1IYpbG6Bbfm6PMdhlqnkKQLEhBjUefjSMJlQZ1uWS-h6cj3GhQheYH3FFMdMMEuhBUgCwi9cHOxeg", "name": "H2O Conservation Technology", "rating": "NA", "id": "30c07988ef8dfc62dac712b9d587daa4a36f2539", "job_title": "Baylor-College-of-Medicine", "place_id": "ChIJIWZRKeHKQIYRXxta3wOMGGc", "address": "1725 Hwy 6, Houston, TX 77077, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.5705632, 29.7714443], "type": "Point"}, "properties": {"photos": [{"width": 3024, "height": 4032, "html_attributions": ["<a href=\"https://maps.google.com/maps/contrib/108143329814504597326/photos\">State from Jake farm</a>"], "photo_reference": "CoQBdwAAAC9nn6jJ6F_RgSlDwM3uP5cHpMqJmQHd_oGKafSj6HbuBt-s4q2LrzRVc92Ks4-TbPLAT_XCz4X9FYPpiXhqEA7tnsqTKEq-Iey1Ral-xxMCbZcLui2raF4DHlQQay2UjcIs6XVdfiRpO-FzxkHST81_LrzkZ4gl_wOJEuYrN8mxEhB4VgkFKSOzxeQNNDuIXr87GhQzDI0yQot1ZpofcoMcJcjWpPi6KQ"}], "types": ["park", "point_of_interest", "establishment"], "reference": "CmRSAAAAlSGk0hARTRsr6V08ldEnPBOWCrFbozavj7NvgUY00hpTpwB8-W0qVCRclZdsPU_-goJeTJtsVt8JQIuLOuvxkXCibTosdPebAw0E_DlRWkGWAksMZQp60fXQ7nTlDpo3EhA_JtUGtA6iGVkWG77aCJQvGhQwtLnprXnGV-w5KOzE2bpWc8_GTA", "name": "Houston Audubon Society", "rating": 5, "id": "050a5458d86bdd1cee7b09678bd6256d0a20a73e", "job_title": "Baylor-College-of-Medicine", "place_id": "ChIJlQOxwVDbQIYR2uX_TZl0TYc", "address": "440 Wilchester Blvd, Houston, TX 77079, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.56820189999999, 29.770778], "type": "Point"}, "properties": {"photos": [{"width": 1800, "height": 1200, "html_attributions": ["<a href=\"https://maps.google.com/maps/contrib/108765250995932379967/photos\">Audubon Docent Guild</a>"], "photo_reference": "CoQBdwAAAMbPfRdN8ZvmgjawIQypZTtJQ04zOchjpplXqV8HqVp7KrinHLjl2U838hrkHnPodsJb3O6H_HSoZJH33_ZVf4g3l2mRZ09B9qS2Ra2RvKGlfgpL9vIUEgWVQZfAL2sJGLqNf_ne1v5zeLdacuiJnpcxXFNuXV9Bo8rj6TeV84eaEhBo0LxPDfLizaiGFTE8INTRGhQTUIBUvDqITaJjT1b_kiZCqOe2DQ"}], "types": ["park", "point_of_interest", "establishment"], "reference": "CmRSAAAAHif3_ctaNFPY6Ec-bdDfQLR6-5QtXwIs1PYG3iBaUcdtC3wTqnEj1qkhXxTgngeSVVEPQTXfl8255G0UYU1agXwCPwhgtd2StDbUQsGgN1IYpTWMkAUYsM0Bf1ZRiIk8EhBmbLuW-QU95jRaTO_EWR9UGhQpbEt4i13PQc5K7LZAnnQ_vft4BA", "name": "Audubon Docent Guild", "rating": 5, "id": "7ddd5daf76cc4979e2ba6b062322d1c77d5d1c07", "job_title": "Baylor-College-of-Medicine", "place_id": "ChIJI9XyNFHbQIYRtwHb8EtTpeU", "address": "440 Wilchester Blvd, Houston, TX 77079, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.44932349999999, 29.7803218], "type": "Point"}, "properties": {"photos": [], "types": ["point_of_interest", "establishment"], "reference": "CmRSAAAAn741If_Q5E3ZGc6H4JQzKe6auIRzYcV-k5N3JyiJ-QQiQiQx5ujUpSnRQIyV_S9Gt2Ovg4o7krZyKROA3DG9jj2zcK9xqBnztz0aspjmUoEOu1EGy0PhyxjHi1xxdN_jEhA3XUco7OOO9SoQvyCMbqQAGhTxEf8EcD1wikCvtOQdcdrN0QkIWw", "name": "Coastal Conservation Association-Tx", "rating": 3, "id": "7258b034e119f31e82320bca6e72781ee9f79d75", "job_title": "H.b.-Fuller", "place_id": "ChIJcekacM_GQIYRPzL13cgQrPk", "address": "6919 Portwest Dr #100, Houston, TX 77024, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.47039, 29.655454], "type": "Point"}, "properties": {"photos": [{"width": 5312, "height": 2988, "html_attributions": ["<a href=\"https://maps.google.com/maps/contrib/101184977609161362375/photos\">aug4</a>"], "photo_reference": "CoQBdwAAALRBMK21dmOLNFWVaR5GIhupOBRfXK7CReiUKJzJImMdH_7bmv5ub9w7MNTKMDi63G84ulmfvKrJVl4j4kEpOxOsMLcYRLo8UM1AO2cdGbYLNtThNr5cx7MFaD_lKYlMpwtdzpXsWJqrAveDpePM3ISk6Hor9dSdjBIk4_p9IRy3EhDFP-obWISr2EMP54YafxlyGhTM4RV5S-HH_tLmHIfDQ4upekp-WA"}], "types": ["park", "point_of_interest", "establishment"], "reference": "CmRRAAAArzkTEGub8Yox5xY4qChxhhdONwf8n23p6atmh9IwArfEINP1eXk9qpcfJQBB5_eQc0cjKSxAFIoqk6HuAde8a3RrWnmnDhiymxFQKRk6nZD4W8Uv5LMYZvnfMcY_a7htEhAx2XUURQ70oWZHbJ1u6n_OGhRmDphR-d93ZQdgGJGzcHpJvrcgrA", "name": "Willow Waterhole Greenspace", "rating": 4.3, "id": "0127506e8071350c2d48f0ca56e939045297a0f4", "job_title": "H.b.-Fuller", "place_id": "ChIJR6_2zTzqQIYRsA7wExgfDWs", "address": "S Willow Dr, Houston, TX 77035, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.4003322, 29.7388505], "type": "Point"}, "properties": {"photos": [{"width": 1136, "height": 640, "html_attributions": ["<a href=\"https://maps.google.com/maps/contrib/117056878997299689379/photos\">Marisol Brown</a>"], "photo_reference": "CoQBdwAAACuE-WS10jobJSY8No2bHP5MKLYEWwCGMRsgM5jg7bIzszc1D37ubgcOlISptekSofaVXStIMqiWKC4wOezb4sDAaHnYifFBAEmAmhX19wGCEmmUY4c_OR0EmoI28dD4cL4zdxo7mL_kouoVR_q7-Ns9y8lWg_0WCHXbs112mZ_ZEhCIPMWUDnd-tbPzoX1GSD2uGhQP7QJsCIRFbu1FFvWjRLG3o3KK0A"}], "types": ["point_of_interest", "establishment"], "reference": "CmRRAAAA61QsnGF36fjuHkkKWzMGc0sR6anO7mAM0-1pE22v651nd1S2SqHjuX3_tNmD6_u6pTIdZziULiIIFrFgyQqBXwoDyHdlqugL1WqPZazb65TtxXICZS_d6Z79rTtMwfBdEhDLM2BQSPS7gKXjTU0kh3bHGhQUwq8XzLG9lYjY2EfI9PzZynMiuA", "name": "Masters Fine Art Conservation", "rating": 5, "id": "a462c2eef4e22ea319485ae7b84f3d20756cbdd1", "job_title": "H.b.-Fuller", "place_id": "ChIJp8u2bZvAQIYRbosnWz6cVmY", "address": "1612 W Alabama St, Houston, TX 77006, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.3876169, 29.794149], "type": "Point"}, "properties": {"photos": [], "types": ["art_gallery", "point_of_interest", "establishment"], "reference": "CmRRAAAA0nrfLG-l8H85fVG65zZGdKiusFNSBhTnEhW77bMyLB8k2iNX0dE57yJpPRDjVN-O6qHm44RvKqi5XCeGrMKEJ1_0ddyU8YW0rM0Od12PWRHCJH0iMs7B0A1L9OZywtowEhDPVUC7NOOtasL20DvVLqyGGhQ4D1EjzktkR507FuVpFrfissN7hA", "name": "Whitten & Proctor Fine Art Conservation", "rating": "NA", "id": "883a8c5ef35ab28e1630235ad65a6b16506a67fa", "job_title": "H.b.-Fuller", "place_id": "ChIJ8YuXE6K4QIYRn1SF1hazFEw", "address": "1236 Studewood St, Houston, TX 77008, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.3858767, 29.7300997], "type": "Point"}, "properties": {"photos": [], "types": ["point_of_interest", "establishment"], "reference": "CmRSAAAArQi96bnR9DGbiB7KHqGiKDA70zyQAcgIbkZeyfkV3QJtNLjpOqVQ48apr-JbzwYgN4ZKxn-LDIAyCT_syEePHwv6JUJ-2Dy7qcurecpZW9RlwKwJY44u8O6EabDb7lEXEhChAgl_CdZrf4S0SSA-b34kGhS1NG8PVhLvbbQfQevQme2o6najoA", "name": "St Mark Fine Arts Conservation", "rating": 5, "id": "ea2d4bac6d74716b33f456dff3aae0cc0b43cca3", "job_title": "H.b.-Fuller", "place_id": "ChIJKbDEoXm_QIYRcRFBlp0dE8A", "address": "4901 Main St, Houston, TX 77002, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.483218, 29.7482286], "type": "Point"}, "properties": {"photos": [], "types": ["point_of_interest", "establishment"], "reference": "CmRRAAAAmVmwYV3qWVnhyVRRMwCTYQwrbM4bJfpChBUO4RNghIZPmy1Cb0QMReQVVd1XW8BW1hM6ywawE9WnQbGyr-bD5Ua0iVrLnABgie5HqdvkPK5ZWOZv0tiBQFndMuccTLwAEhAFM-r9sO1SfE84EH-2RetPGhSvogU8trQyZk7u5aOVF5MkaYrqWg", "name": "The Nature Conservancy", "rating": "NA", "id": "90af6fb9fb926dde9f7103577cebc4150bbb1dec", "job_title": "H.b.-Fuller", "place_id": "ChIJq-m4EX3AQIYRJkn4Lhccp2E", "address": "1800 Augusta Dr #240, Houston, TX 77057, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.42318089999999, 29.7345943], "type": "Point"}, "properties": {"photos": [{"width": 750, "height": 437, "html_attributions": ["<a href=\"https://maps.google.com/maps/contrib/106788706324997826205/photos\">Erika</a>"], "photo_reference": "CoQBdwAAAMCXZ5c7Fdopx1_r7TADZGmoqLBmjKTr-mWp2JIXW6scP7312hdgZGUPze2pv-5k0EAirql6F_1kR3PzoIvihGsr2RsORbpgW7W3zOBpa4decwLMrUSraV1nljfIuRYoivW4azjcbDKxpElX3STNcrWlevmwdpjSftjXBquMPWQZEhCPIki2MIwslrndiIe9CNA8GhR5jF9yKcfC2QDN65BFEWBJyJ6hpQ"}], "types": ["point_of_interest", "establishment"], "reference": "CmRRAAAAn855lLXcaFv2cDPLAZgVHELJzpQSjvPbQTeowmSzMwRLN0L511iAKV8eMPEMjY_w8Qhq1UMB8tBjRtHUMS051qJWkzOkpd6vldsiCEGF9gGcZxbVfIV-RT9UjkMlFyjuEhDd5TtSTiuyUAbMKZgmojZyGhS3KcL2WJ-EEGMWgEbZr0jMni579Q", "name": "Student Conservation Association", "rating": "NA", "id": "1c5ea7722fc0d99e9f7dfca55f5d9078224d51d3", "job_title": "H.b.-Fuller", "place_id": "ChIJQcqBXfDAQIYRErawO-goGj4", "address": "2990 Richmond Ave Suite #400, Houston, TX 77098, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-96.038102, 30.055621], "type": "Point"}, "properties": {"photos": [{"width": 984, "height": 985, "html_attributions": ["<a href=\"https://maps.google.com/maps/contrib/110279808588468038448/photos\">Peckerwood Garden Conservation Foundation</a>"], "photo_reference": "CoQBdwAAAMivM027qkBpG-l9_Am4y_bUzcgCEmbLBX3cpPSnRJ7Wz1vOHwGxcu-nCRDMTf8-FGnzUvSICUTGtfRlgjAqyKXTv2VQ_YBsdZSU0KhDD-UxN27sDMvLLCTEf6_ZSydRC-0q1coMsKXMFzCZhn3pjEUCap3XjwIQ6c5yn8vAqNLuEhCUqO1Z_8l-cs0pvqLs3xf4GhSS5LYMgfcVMOc2FpMOPDrWmc-LIg"}], "types": ["park", "point_of_interest", "establishment"], "reference": "CmRRAAAAj7klVcllKDvbOxaNthzse1e-V2TPLp0ly1ed7WPexFvwtYRMMJkGOB8CqsYUCR38VOA8KnrNlZ5hB-aPuH7_pBLpYLixkL2RnJMVaMikjjMoEZbbCiwXgPNY2ObOv13sEhDqbkIqPvtAmNaLyMXa4gZ_GhTFtMlnb0YBjrcn97X6xL1zTqDUHQ", "name": "Peckerwood Garden Conservation Foundation", "rating": "NA", "id": "e618a4c618cd67ce4f5fdc165f640220ab3b53b2", "job_title": "H.b.-Fuller", "place_id": "ChIJmUR7pvHKRoYRIIl0o73bPGE", "address": "20559 Fm 359 Rd, Pine Island, TX 77445, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.64386449999999, 29.7515036], "type": "Point"}, "properties": {"photos": [], "types": ["point_of_interest", "establishment"], "reference": "CmRRAAAAHpSI1BJwcvLoE7kVORz_W_Uyd9go5_RCyougjEGVfeoDSYuKBLun5GnegBkIGDZOqOi_QMZ5to7-Gg3MoKtTuSei9ZYKqXOCw9QXWBVR8049qUEoDYApkk2GVhFZQynUEhDkkCi7_ofOSACMEufOGfNKGhS7vAEzHfbvZ6FOF1WLpjOYWw67qw", "name": "H2O Conservation Technology", "rating": "NA", "id": "30c07988ef8dfc62dac712b9d587daa4a36f2539", "job_title": "H.b.-Fuller", "place_id": "ChIJIWZRKeHKQIYRXxta3wOMGGc", "address": "1725 Hwy 6, Houston, TX 77077, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.5705632, 29.7714443], "type": "Point"}, "properties": {"photos": [{"width": 3024, "height": 4032, "html_attributions": ["<a href=\"https://maps.google.com/maps/contrib/108143329814504597326/photos\">State from Jake farm</a>"], "photo_reference": "CoQBdwAAAJoWHfoASRvkIEato8LOfLPsVbV8kVhCy15ZgQowiM5Rs5gdx2uGZXT9D_rv1B9ZU3I96kVbsKxIxftF0vOMV6UwWDBMQnLzqvUWWl7n3e73WdDHcoes3rfMtMMFf8Wwgp6c3KNvo6usA3xZiZ521QAH5Ctc6fbZ0mhxW5ML4ca6EhDdLja5EK0LfWUdxlXUjaHJGhRyAkoAGLws6_daHoNPDoQN9USfZw"}], "types": ["park", "point_of_interest", "establishment"], "reference": "CmRSAAAAO7eTxNTq_bbrJsgnLakHBPIQdAu5MoCR2KWwQ2u9CAoVeqci1-KXdxsyfoBac3OnvJG3t3HjMcnGXY1tGA5by8EgYL1h3i26Ty4jMfDR2CmJzUkN_Hy-WzpcFVamdpo1EhDhdXoIH1Mhg8C0EHgZtOccGhRNItGCHul5sYsDWbkn512Fx1Lltw", "name": "Houston Audubon Society", "rating": 5, "id": "050a5458d86bdd1cee7b09678bd6256d0a20a73e", "job_title": "H.b.-Fuller", "place_id": "ChIJlQOxwVDbQIYR2uX_TZl0TYc", "address": "440 Wilchester Blvd, Houston, TX 77079, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.56820189999999, 29.770778], "type": "Point"}, "properties": {"photos": [{"width": 1800, "height": 1200, "html_attributions": ["<a href=\"https://maps.google.com/maps/contrib/108765250995932379967/photos\">Audubon Docent Guild</a>"], "photo_reference": "CoQBdwAAANNeENDWBiBN9Sh4e4uX8FW2IrFjfS7diG72CLsmS6Lmwiu5qJuRH9PpNMuZW84ViDvVoPClHLF6w8uPQr1GAjq7qGKECF2XpIOgqSYnwGzPpMIRf1fFA-4X6-8w-8-yTVrpNS-QV_WKWTqz1vy6ADZ_vZskp4cI8cjWER_-jsuhEhB9QScetiuprL-NSA10sOGVGhTEsVs5NBNQ5QBlAP9XwObEMG2xiw"}], "types": ["park", "point_of_interest", "establishment"], "reference": "CmRSAAAA3dt4naZCWNK2BSadgHUio0pmqDmYrJsiFLXuvR9tP6FDAjHx1lMORhoixx3C92NEFBppzqUzfIMexYzRqqWUv9rOOFx4zbI6diIUizJxJaFExnn5aMiGAcEpuaQ5SspHEhBFroqGD8eOY0d83EIb6DJ8GhR446hEYIwfizu-wvzil0y1euvNYw", "name": "Audubon Docent Guild", "rating": 5, "id": "7ddd5daf76cc4979e2ba6b062322d1c77d5d1c07", "job_title": "H.b.-Fuller", "place_id": "ChIJI9XyNFHbQIYRtwHb8EtTpeU", "address": "440 Wilchester Blvd, Houston, TX 77079, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.44932349999999, 29.7803218], "type": "Point"}, "properties": {"photos": [], "types": ["point_of_interest", "establishment"], "reference": "CmRSAAAAIxIZEhukPboLLRRlIDd2x0RMI-3r4gK6xF4NJJBqnOXJu0PVb8zR6Qvsq0kXqoGMH6IuFv9ZKQJDbwGwNe9Y3O4b-nWcPAcEANXpJ_ZKj6bN5NLqwZHP1y-4xkPPju8QEhDT1KcJWyQsQp34nauvvrGmGhRkoFKoCXj78CGUzK5OVud4DYV5SQ", "name": "Coastal Conservation Association-Tx", "rating": 3, "id": "7258b034e119f31e82320bca6e72781ee9f79d75", "job_title": "Roto--rooter-Plumbing-&-Drain-Service", "place_id": "ChIJcekacM_GQIYRPzL13cgQrPk", "address": "6919 Portwest Dr #100, Houston, TX 77024, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.47039, 29.655454], "type": "Point"}, "properties": {"photos": [{"width": 5312, "height": 2988, "html_attributions": ["<a href=\"https://maps.google.com/maps/contrib/101184977609161362375/photos\">aug4</a>"], "photo_reference": "CoQBdwAAAEsKL82nC9mtWXPDu9gtQuN4vWAgNNtNkO0VfbadmD5_wGAZli1Yg4igCbcavGY6e7apgHq2qSe-KXj1wbW8LrHYX9_L_bw_CzZakPda4Lx0KdjNoaxY36syQRsms-Dt4AwA6wpntw1E3KGYI1XZl4qtQOzK-JTr4_sB49u_HHhVEhCh8C0MambBduo_v0Kmd-KTGhSdJLkSwJVG2QujIM6EOjBv5zED3A"}], "types": ["park", "point_of_interest", "establishment"], "reference": "CmRRAAAAtP1-LSC_BDEGoOMRkXRD7DKNfy2kUautfkAhnKHWxYvXO6cBZLzdIDpzqioP0XIefs2GlVj6ubvHhyWZ4NmWVTnxPn7-ihSHJB9Ng01mJi365mGC_H8OfqfcjTFnr5ZUEhB1ddxx91YePaW8AnR_LwLXGhTaoF3VC6SC7feRWN0RYQrmVEOXvw", "name": "Willow Waterhole Greenspace", "rating": 4.3, "id": "0127506e8071350c2d48f0ca56e939045297a0f4", "job_title": "Roto--rooter-Plumbing-&-Drain-Service", "place_id": "ChIJR6_2zTzqQIYRsA7wExgfDWs", "address": "S Willow Dr, Houston, TX 77035, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.4003322, 29.7388505], "type": "Point"}, "properties": {"photos": [{"width": 1136, "height": 640, "html_attributions": ["<a href=\"https://maps.google.com/maps/contrib/117056878997299689379/photos\">Marisol Brown</a>"], "photo_reference": "CoQBdwAAAKPJ1gfIPWhZARsQEibEM2_gqZJDnrVV-C46tXrQaaClnjl-FyXjddykjvHJhRArAgljAv_B7kjA6YdaHK8q0yZOiKe78uDSoUTeiMBIhWNczyeI1KLWIycjHrm14u-UPevsNk4tL2tyzGTGTcd5lCNdkvzi_X9Le7Hsg1Rq2JFMEhC3s0HpmDfjIfn4Q_QY6XwPGhStVGIWkUqFUdnC9cYTP8Xh7nRQTg"}], "types": ["point_of_interest", "establishment"], "reference": "CmRRAAAAIgOojxUKxWQ4jgMW8xpda3kTqWOaBRwFIPnZILlI-JUxkcH66wAb-PnZfHb_-gLX3NLAy3g45MP3YTahmfl92J4kFyY0yenlhRBCWL6Q1ZViZkyAGJTAxRQA6oG8WQs7EhDPm3NpU29QyoR57Rn8X1GMGhQN3d6DbvjppJ7WwAfS5lfGkVrMKg", "name": "Masters Fine Art Conservation", "rating": 5, "id": "a462c2eef4e22ea319485ae7b84f3d20756cbdd1", "job_title": "Roto--rooter-Plumbing-&-Drain-Service", "place_id": "ChIJp8u2bZvAQIYRbosnWz6cVmY", "address": "1612 W Alabama St, Houston, TX 77006, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.3876169, 29.794149], "type": "Point"}, "properties": {"photos": [], "types": ["art_gallery", "point_of_interest", "establishment"], "reference": "CmRRAAAAyffM3tKYpCMPu7fzj1xZyqsW_jFhov73iEdxDXDFYkp5JEJnTe2RGd8c_PHfcYfPIwKyjl6ZdNYUnnmKjbKaSfIxT3Z4OLo09wq8DOZkxhJ0RSv5pSmFbxpHMBj_SAlsEhCIToEIFFHhua9oWc4_Yh8MGhRE2kU1q-cekZWwU2xKL9lPAIgfQw", "name": "Whitten & Proctor Fine Art Conservation", "rating": "NA", "id": "883a8c5ef35ab28e1630235ad65a6b16506a67fa", "job_title": "Roto--rooter-Plumbing-&-Drain-Service", "place_id": "ChIJ8YuXE6K4QIYRn1SF1hazFEw", "address": "1236 Studewood St, Houston, TX 77008, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.3858767, 29.7300997], "type": "Point"}, "properties": {"photos": [], "types": ["point_of_interest", "establishment"], "reference": "CmRSAAAAJxOTcg1nnarEJ7lafqfZDBHlYLF-gV2yb_U53_jAaq6VY82znaKrw2RmTfsMJXNHdL4TSiuCnmmoNUQ72VkMyKTcvxURhfayQleVpOSxDIS7q7KQt9h6Cl3SqfE82qy5EhDQlpYU3CMGHJiGfkoNJHFsGhSeYrvdCpM0eG9FqGEG6pDINT9zWQ", "name": "St Mark Fine Arts Conservation", "rating": 5, "id": "ea2d4bac6d74716b33f456dff3aae0cc0b43cca3", "job_title": "Roto--rooter-Plumbing-&-Drain-Service", "place_id": "ChIJKbDEoXm_QIYRcRFBlp0dE8A", "address": "4901 Main St, Houston, TX 77002, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.483218, 29.7482286], "type": "Point"}, "properties": {"photos": [], "types": ["point_of_interest", "establishment"], "reference": "CmRRAAAAotyTAlcgoTzKZ-maeWWJUQXw3_qAUICh0879UB47fOZqaQa5Af4T6fjJ1rWJ83GkcBx07dD3cLJ88ycrGppe2_u2n6d64Kug4lC-yURykFNmnyXNoBTI1JYdm0Nrq6W8EhCocDs2eYPgFs3sOcCDNSLxGhSUUJKyNHCHyzq0eM1N6hO7s1m45w", "name": "The Nature Conservancy", "rating": "NA", "id": "90af6fb9fb926dde9f7103577cebc4150bbb1dec", "job_title": "Roto--rooter-Plumbing-&-Drain-Service", "place_id": "ChIJq-m4EX3AQIYRJkn4Lhccp2E", "address": "1800 Augusta Dr #240, Houston, TX 77057, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.42318089999999, 29.7345943], "type": "Point"}, "properties": {"photos": [{"width": 750, "height": 437, "html_attributions": ["<a href=\"https://maps.google.com/maps/contrib/106788706324997826205/photos\">Erika</a>"], "photo_reference": "CoQBdwAAACcdXyr_PClFzUBKzvF8tl7-nqw09wDPsr4auC8BAxHG-IZN5PQu92pZwfUqtTfLG-gFb5s_ZD92YeuhE6jwpmjycr6NcIEZ1ZODBcubYC7gQwcgxQQz05x33H8Ds-KbBPzMntxpqxh5IWMUdXPoN5K8MMRuerLCu5Ys5UgxOPmNEhBann81JEvlBOUTfB8V-MTuGhTOoIO7P0qHsxVjUGQKBqDHqVSD3Q"}], "types": ["point_of_interest", "establishment"], "reference": "CmRRAAAAVNFqxcuoOLJi2P4iB9mEAXZ93g2TLtnc-oebLVwQYQxPeU3Iwdx2OehbOJ1772B19U5KL3VJZqO6Zms01HMPjb6JmjLTdqL8omTDeKn76_c8KxFH7_RigvkoSN-MP8BMEhBn0NMteNF8_GT4JmFDK9MhGhSnAJB-Ino95LBWKuJP_BfMaYU1FA", "name": "Student Conservation Association", "rating": "NA", "id": "1c5ea7722fc0d99e9f7dfca55f5d9078224d51d3", "job_title": "Roto--rooter-Plumbing-&-Drain-Service", "place_id": "ChIJQcqBXfDAQIYRErawO-goGj4", "address": "2990 Richmond Ave Suite #400, Houston, TX 77098, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-96.038102, 30.055621], "type": "Point"}, "properties": {"photos": [{"width": 984, "height": 985, "html_attributions": ["<a href=\"https://maps.google.com/maps/contrib/110279808588468038448/photos\">Peckerwood Garden Conservation Foundation</a>"], "photo_reference": "CoQBdwAAAOZaZ8dT_E9EazhioaDPTZEtMgVDXaW9ua6pOQsJbkL_lfvpkiw3DRO7kRJsnHnYECwcnHSZOL3bXE8SucBTj73yefyN17jLeoLPek1St2cpkODJKwWe4I1mBIS4Czdr38rwEbf44-7aBFVk8HmTZFJcQiQnEuo6HnPfhFvOAKA8EhBc0RND5-elw_vFvRZkuPD7GhSZNajpu9MTDJFrHbAPw_56_UK-Ng"}], "types": ["park", "point_of_interest", "establishment"], "reference": "CmRRAAAAB5tx-nIDXshLEm_GPi1UIwRPHKsDOMUnnE2xwH5mKUkb7RV3Y2c8ByQBlJqqYMHZ3TR_97s8ugKn-u7f5EBU_4ykIBbvs-s621SHKQFEv_J5ulIR5JgBiu9kYPVcOes6EhA3qh9LFk3ASoV7mOiWG-dJGhRqzzKHwEcwBRxB7cCE8nnMxuE9Xg", "name": "Peckerwood Garden Conservation Foundation", "rating": "NA", "id": "e618a4c618cd67ce4f5fdc165f640220ab3b53b2", "job_title": "Roto--rooter-Plumbing-&-Drain-Service", "place_id": "ChIJmUR7pvHKRoYRIIl0o73bPGE", "address": "20559 Fm 359 Rd, Pine Island, TX 77445, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.64386449999999, 29.7515036], "type": "Point"}, "properties": {"photos": [], "types": ["point_of_interest", "establishment"], "reference": "CmRRAAAAQe-qujV3cvHz8jkTszW8D1XAg8KW-FvpYcb08jWUrDVN3gSGZKfqjw4Aap6Wzg0OfWIk5ctkqfwmR_kuCrABJYo0RK8vGileBB5xw4DaadjqTIGW_cMT7b4GfsQ712LpEhArImkW9t8qitxNlGYpm0AiGhR-C6iWqJaSPhS0P2uBFWy2r4a77w", "name": "H2O Conservation Technology", "rating": "NA", "id": "30c07988ef8dfc62dac712b9d587daa4a36f2539", "job_title": "Roto--rooter-Plumbing-&-Drain-Service", "place_id": "ChIJIWZRKeHKQIYRXxta3wOMGGc", "address": "1725 Hwy 6, Houston, TX 77077, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.5705632, 29.7714443], "type": "Point"}, "properties": {"photos": [{"width": 3024, "height": 4032, "html_attributions": ["<a href=\"https://maps.google.com/maps/contrib/108143329814504597326/photos\">State from Jake farm</a>"], "photo_reference": "CoQBdwAAAANqu6fGBYpcdd1hyBhwuhInA-x769V58_7XdnC79eSpZqv9JolqsVTA8K3VNEo2hm0o9XsJNZGhndh0gJiKr5kqiOlgg78iLuRBexq1ftqxKrNX9Agc1WkbcKo0mqHT6KfSkaV9ktCCDGT6hRtngRCDE0xWhFkz1HZMKze5n6kuEhAa8vkklosnur7arsrgUU5TGhTHNh5av_qMbYr-Jze1ynDG6vXyLQ"}], "types": ["park", "point_of_interest", "establishment"], "reference": "CmRSAAAAfhKh_6kpDLBVqLHXwvtcPWwAMJ92VpMSuENiuqryZMjIY1xfR4y6glkgOM8DO6YmR17IQMmJcAwK-ajLZX0rtu0dhtkx7Vz8JLZ72Rm-_6CTu_velRXQbEh1Lpy-Xhe6EhC-NeOGoh2hg72qsIczy-_TGhRhZ8gdowPTgDG79r8U5ZXpvuKaFg", "name": "Houston Audubon Society", "rating": 5, "id": "050a5458d86bdd1cee7b09678bd6256d0a20a73e", "job_title": "Roto--rooter-Plumbing-&-Drain-Service", "place_id": "ChIJlQOxwVDbQIYR2uX_TZl0TYc", "address": "440 Wilchester Blvd, Houston, TX 77079, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.56820189999999, 29.770778], "type": "Point"}, "properties": {"photos": [{"width": 1800, "height": 1200, "html_attributions": ["<a href=\"https://maps.google.com/maps/contrib/108765250995932379967/photos\">Audubon Docent Guild</a>"], "photo_reference": "CoQBdwAAAFazSrFNTnCUJXt2UgdkVVNoiDB5LsNyTs7fnMLQinSAvsoheIUtiKHtve-YI4XI5ChrkWNztkr3xqD5Jcr_73YE50LbsVCZ_2V20jp8XYk8k6S6S9O7okP-0wB3cup_sq_q5nVGX9XRxrye799tygcDkurlqAkQ9GbsDsgSmODrEhBJDdCWPAuczTpyngwxEg7bGhRxCNX1f68_ntWPw-1AmPLoftW6ug"}], "types": ["park", "point_of_interest", "establishment"], "reference": "CmRSAAAAlbVk-SgUed6rcHpuzkfqfOcxGn4etIplxaYne7E6G9cWbbINzsuhTImc4A2-6RrvBcbyI-DQHiGXzb6B_0_28UEwU-HvLKJyHL0JbmZvlm_WBJqrb_gouyTZZ0a_BMAtEhCP2W05ZV6d_pdUYlHUmxpSGhSSq8nMAIu8gBGhPpLCZR5CCheh3A", "name": "Audubon Docent Guild", "rating": 5, "id": "7ddd5daf76cc4979e2ba6b062322d1c77d5d1c07", "job_title": "Roto--rooter-Plumbing-&-Drain-Service", "place_id": "ChIJI9XyNFHbQIYRtwHb8EtTpeU", "address": "440 Wilchester Blvd, Houston, TX 77079, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.44932349999999, 29.7803218], "type": "Point"}, "properties": {"photos": [], "types": ["point_of_interest", "establishment"], "reference": "CmRSAAAAPBHsIMVImHUMWORVc-FFmMe7vAf2I3vjVcpB3vXvyVEO33tel89JLktkAoOy1XRt9h6KO4A4JOItGowr91gyCGzQ6xuP5Poi_aITLk2cLNzMPJyxQvmPM9IvRtI5Sj8FEhCax93yY9ZvlvxnAuXqYjcbGhRdhM1Y4AEF363WFFwcrXklPUm2Ow", "name": "Coastal Conservation Association-Tx", "rating": 3, "id": "7258b034e119f31e82320bca6e72781ee9f79d75", "job_title": "West-Inc.", "place_id": "ChIJcekacM_GQIYRPzL13cgQrPk", "address": "6919 Portwest Dr #100, Houston, TX 77024, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.47039, 29.655454], "type": "Point"}, "properties": {"photos": [{"width": 5312, "height": 2988, "html_attributions": ["<a href=\"https://maps.google.com/maps/contrib/101184977609161362375/photos\">aug4</a>"], "photo_reference": "CoQBdwAAAOsCYtSUYnWMSuIqP2BZzztx-kE3Du1OJYSMzWCkzXnBNskeC4H--RXRImP587crOZhW2-g6RbUl6Qtnb4AokQ5iugmGi-3WWHYqb2KM1N8yMSkstrBnR77vGaz-kAwlfkWtCny6jy9KOV4JHDLcA7Bxnq67rIB_q1GiA6mV-ghBEhD4MrdwUk0HksmBy08IHI2eGhTZ0uaaZOYmOeeZkwvlpXsj0MxomA"}], "types": ["park", "point_of_interest", "establishment"], "reference": "CmRRAAAA5QM0XaUJ-XWsAcTNhk-2t0N6zdutwCs3oe2brbBk9qcB23Rz02eJFcBq550Mm_Q46uF62CFDZyzzajNxG3rL7QbB8aTjdNLXUZTwUH-V6Ik2FHryxg5cYzag4FIYcJacEhBs07R6NMam8D3O6QrjiTnRGhRVA2D0FabXYov7eBY9K6RlrDl_ag", "name": "Willow Waterhole Greenspace", "rating": 4.3, "id": "0127506e8071350c2d48f0ca56e939045297a0f4", "job_title": "West-Inc.", "place_id": "ChIJR6_2zTzqQIYRsA7wExgfDWs", "address": "S Willow Dr, Houston, TX 77035, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.4003322, 29.7388505], "type": "Point"}, "properties": {"photos": [{"width": 1136, "height": 640, "html_attributions": ["<a href=\"https://maps.google.com/maps/contrib/117056878997299689379/photos\">Marisol Brown</a>"], "photo_reference": "CoQBdwAAAIkO4iisqUFopiP3CAF75bej-SzHmWNPNnoJWE3SbX1D3OMmDTLueWhYuFVgnCmi8F_jGaaTByDP6d9KuatBxV-gnKybB37WBPxM6kwXjKenvqrI3K4XSeui2yf1osDibL9rjKtGQ7dL-cZMFflWseVkQSdTRFYbKiXXvVYHrUEgEhDQPpGv00siq5Av6UoliQXUGhTHE-ADEXz8n2Oi46u8Yr5H9MF9mQ"}], "types": ["point_of_interest", "establishment"], "reference": "CmRRAAAAw-plzS5gMFDwInHzU8aYbOJEfzVm4lF-s9ySMcbxG0OX93HcbL6aEjdCKhChJBsCDF_sP6mLKIgWRzYI8mFsIPcJLp5n734NJUbC641-vtg-sZkk3AqW6jcfFuMFoCtkEhDbTxBo8QkfiHYE_Qb2aNb2GhTiWk0YaF_2rd9MJo2ZrsKeZOYRag", "name": "Masters Fine Art Conservation", "rating": 5, "id": "a462c2eef4e22ea319485ae7b84f3d20756cbdd1", "job_title": "West-Inc.", "place_id": "ChIJp8u2bZvAQIYRbosnWz6cVmY", "address": "1612 W Alabama St, Houston, TX 77006, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.3876169, 29.794149], "type": "Point"}, "properties": {"photos": [], "types": ["art_gallery", "point_of_interest", "establishment"], "reference": "CmRRAAAADq1Tc8QU-V9Cy_ooF1ZmONCcETI1jJ-jHMTVwJefUt4qht7dzOdO2Ij3h0i_z1RGh2CtPNAzyciPH7ANdFJaiDkgRqt5z6CinbGsnbr50CdFPONvT1fxdqHLe1erxtPVEhA3__3pPMv6lGRCjeS0smyVGhSSCxqT_6lTIshjgKAfO_LbTkrztw", "name": "Whitten & Proctor Fine Art Conservation", "rating": "NA", "id": "883a8c5ef35ab28e1630235ad65a6b16506a67fa", "job_title": "West-Inc.", "place_id": "ChIJ8YuXE6K4QIYRn1SF1hazFEw", "address": "1236 Studewood St, Houston, TX 77008, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.3858767, 29.7300997], "type": "Point"}, "properties": {"photos": [], "types": ["point_of_interest", "establishment"], "reference": "CmRSAAAAvjpWQt-gyo_VCoLc9tzHOCGZmOdqmPyWbm9-n1foNSzvjjtA9yOf-Ojj32woVPJ-QOBu4dYDZopu5GXV2pHZYIa2sD3M2Vm0egBXEIjcvnvPdXo9c0ty5zvRtE2TKgXtEhDzTcQ3IZCHG_XxPBRUpzHsGhQIU0ZHTYaTQj1fJRQLWm86FHU1ug", "name": "St Mark Fine Arts Conservation", "rating": 5, "id": "ea2d4bac6d74716b33f456dff3aae0cc0b43cca3", "job_title": "West-Inc.", "place_id": "ChIJKbDEoXm_QIYRcRFBlp0dE8A", "address": "4901 Main St, Houston, TX 77002, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.483218, 29.7482286], "type": "Point"}, "properties": {"photos": [], "types": ["point_of_interest", "establishment"], "reference": "CmRRAAAADVATRkwqdFrQAacs195wxuJ1Pgo_NENxy2neRm6NolPRYbU4IVetHhen3t_hpkEIiNN8x397lB7ib30YsR-VszjaGWj8rQJ7mR3QX1xCnLSRxZgz_0Sb-k4lXX5MawwkEhCzVODwLZJ6rdlI3eWKph5jGhQJqjFl2bEO0nHjm5HdTd8QxSCX7Q", "name": "The Nature Conservancy", "rating": "NA", "id": "90af6fb9fb926dde9f7103577cebc4150bbb1dec", "job_title": "West-Inc.", "place_id": "ChIJq-m4EX3AQIYRJkn4Lhccp2E", "address": "1800 Augusta Dr #240, Houston, TX 77057, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.42318089999999, 29.7345943], "type": "Point"}, "properties": {"photos": [{"width": 750, "height": 437, "html_attributions": ["<a href=\"https://maps.google.com/maps/contrib/106788706324997826205/photos\">Erika</a>"], "photo_reference": "CoQBdwAAAH5gPVjW_ZPOUdlcF83ITSM6my60Cd4bj-YTSQmauYh7FZQx4jaKlXhW40QAQr8ktstEcIYAjRGrkHFzo58UMlsfl72w_IfaFvyD6hb0TEqcfRKQIcwC1ghBULCiNJTyWiGCFZ3T-gYRuhy0NeK0xxgbVDzDYBe6Z4q6j8-Q-SUAEhD5Yo_r9rAyhyTOSphO3IGMGhQs2gVAMiDiVlQNICbgUr9u1TsI4g"}], "types": ["point_of_interest", "establishment"], "reference": "CmRRAAAAYQ7b5uR0WwQqXRUN6-HNvDg4AXPFhs8aVEZ-CKhI67aoJEKjarL3AYcLtL0kHcOvaarw28_NO7cu4wWc-3j7Ty_xU3ForL4NZFM8jJp5NgtqQ4rdrjb1iM7isaqEJnipEhAnR_3Z8zDTyaR0Eetz1okiGhT2PHA8Xf5a1UEAxdfjitTJOCMOnA", "name": "Student Conservation Association", "rating": "NA", "id": "1c5ea7722fc0d99e9f7dfca55f5d9078224d51d3", "job_title": "West-Inc.", "place_id": "ChIJQcqBXfDAQIYRErawO-goGj4", "address": "2990 Richmond Ave Suite #400, Houston, TX 77098, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-96.038102, 30.055621], "type": "Point"}, "properties": {"photos": [{"width": 984, "height": 985, "html_attributions": ["<a href=\"https://maps.google.com/maps/contrib/110279808588468038448/photos\">Peckerwood Garden Conservation Foundation</a>"], "photo_reference": "CoQBdwAAAN41wTKw8Ubj2PnopMEp9SG69DbYeifLRoxC_WL9yuSyyyf47bLzKDHOyA7qdWRABhjh2gkIBCaWnzSzV0jTrtFRZcBRqh0RqUWfUjQ1hyPqtyXx31Gp6gJVW5yYSvvuPr5Fp7I7VvGx3balDQVBYQQB8YK3pqxPkHFiMkwVtKxlEhCMXfU9GO0FjtJ1HhNDBq5NGhSYuL_YSZyFLMI8RuavuFJ4b_eyng"}], "types": ["park", "point_of_interest", "establishment"], "reference": "CmRRAAAAaCOoifObvotQkxksLTGglAdjZb2xpeIVQ7bcTTBpZd0CxtZVs84fayIrqPogcL4tnEEbxAkymA0ccixclvIQdfh8vOedJ-1HHzpw2qDMjGFAiAzBV9bopyfWFUCcLh3nEhA7b1x33_7GMs3p4gqjpVSZGhSk5Ia_GTn1tXj-M1yqM7AAKpCcqA", "name": "Peckerwood Garden Conservation Foundation", "rating": "NA", "id": "e618a4c618cd67ce4f5fdc165f640220ab3b53b2", "job_title": "West-Inc.", "place_id": "ChIJmUR7pvHKRoYRIIl0o73bPGE", "address": "20559 Fm 359 Rd, Pine Island, TX 77445, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.64386449999999, 29.7515036], "type": "Point"}, "properties": {"photos": [], "types": ["point_of_interest", "establishment"], "reference": "CmRRAAAAbhonTSo7P6Tg8XE4zVDVh799yJtmly1U0vDioQxXnN--8Pn8DrGl069EFNJ872qXK7c5ehFI6CPKyd9l0dSLb2vP2h448pclXta-zthhKx8rvao-3d7RYSetaz9WNZFnEhAmASqHrYle6VVLjA0i8wWqGhR0iZd6mb9iz0caqbUlCdfaUB7H3g", "name": "H2O Conservation Technology", "rating": "NA", "id": "30c07988ef8dfc62dac712b9d587daa4a36f2539", "job_title": "West-Inc.", "place_id": "ChIJIWZRKeHKQIYRXxta3wOMGGc", "address": "1725 Hwy 6, Houston, TX 77077, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.5705632, 29.7714443], "type": "Point"}, "properties": {"photos": [{"width": 3024, "height": 4032, "html_attributions": ["<a href=\"https://maps.google.com/maps/contrib/108143329814504597326/photos\">State from Jake farm</a>"], "photo_reference": "CoQBdwAAADb_35bdvjeFHcfAtt4rSMw8_yAkat_wwyFIuD6TI2tV1rM4ZTPbQSc5QNI81BWYb33IDb09KgfEcdRsuEUGCfmapHLkX0xA-Jg1fvzAqN3yci42uqEgP1hQ_EDOgSU6rpOei_14tBHspWJW0xICAOQDAt23iErcLQXjPWDbtb_-EhAZLF2ZvLILp1sgF0eU_omaGhRSgdBIDwXip7iTut9tVHdPddARBQ"}], "types": ["park", "point_of_interest", "establishment"], "reference": "CmRSAAAAy2200g3vzPC2DyFID_XcTL0_8o2unif9pgbF1mQdLJ9l3kYKzfUZzreI7mGZYWnGRw3dopq0tm3z141P7oI6xulWBX4CcxdY1BBtaSoxb_Di4enDYzCnAWP6RV_2jaVAEhAXuLO2E3h_aoHOUwbaLBMUGhQpeH107XfbQwACI0gKB1HP9Qibsg", "name": "Houston Audubon Society", "rating": 5, "id": "050a5458d86bdd1cee7b09678bd6256d0a20a73e", "job_title": "West-Inc.", "place_id": "ChIJlQOxwVDbQIYR2uX_TZl0TYc", "address": "440 Wilchester Blvd, Houston, TX 77079, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.56820189999999, 29.770778], "type": "Point"}, "properties": {"photos": [{"width": 1800, "height": 1200, "html_attributions": ["<a href=\"https://maps.google.com/maps/contrib/108765250995932379967/photos\">Audubon Docent Guild</a>"], "photo_reference": "CoQBdwAAADLko8ROxgNaLJT-6TC8PpQ43k5F7wMwxASp_8h28ewtdG_3i8WszMTW6QGO1ZF1FT_AK-birWVYRVofD77gnx2SMpMBMt2ngT-86LzMV5Vn6sepxLg9uSUMPa0QlawhMaxTz-lEALCHdib5mfJ0RlvTDnfe0Uhy0xlbEdUh8NO7EhA6WELen1-jfQDtrZi4LSrUGhT-6kZmjSfZ7gBTpbQkAdhZ4U3d4Q"}], "types": ["park", "point_of_interest", "establishment"], "reference": "CmRSAAAA63Ks_46gtH1UBHoZq1mA074YbSndL7zVW5zk5bB6v6zpj6S3IlpXQjnMVW-Lb6bpqYtC958aLml6uxWn8jSJ6KW9Q8CTBiFvgfdAZlKMO4RnQ-06r2emXPEH4iHoH57hEhCX33Z-rjwN8aErlyHI4F4SGhTsMoJgqjaFPV8uIfwIh7xlpR-pvA", "name": "Audubon Docent Guild", "rating": 5, "id": "7ddd5daf76cc4979e2ba6b062322d1c77d5d1c07", "job_title": "West-Inc.", "place_id": "ChIJI9XyNFHbQIYRtwHb8EtTpeU", "address": "440 Wilchester Blvd, Houston, TX 77079, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.44932349999999, 29.7803218], "type": "Point"}, "properties": {"photos": [], "types": ["point_of_interest", "establishment"], "reference": "CmRSAAAA5iLPagLRwqzAzdG-wuay8I63F4TQabjAU13qxJ_9J6WqNAgsPnI-HLwdH4hS8VuEmP8elHWJaOnWcWEGWdwizvRxj4gTeaMzRyIuhBsH6f_l421dxALASiy-o6koyUshEhAlfKE3JfcJ5QR5bqzoqFAVGhRrKRPR1Dh1fUpOu7YnF_jqd4ontw", "name": "Coastal Conservation Association-Tx", "rating": 3, "id": "7258b034e119f31e82320bca6e72781ee9f79d75", "job_title": "American-Midstream-GP-LLC", "place_id": "ChIJcekacM_GQIYRPzL13cgQrPk", "address": "6919 Portwest Dr #100, Houston, TX 77024, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.47039, 29.655454], "type": "Point"}, "properties": {"photos": [{"width": 5312, "height": 2988, "html_attributions": ["<a href=\"https://maps.google.com/maps/contrib/101184977609161362375/photos\">aug4</a>"], "photo_reference": "CoQBdwAAAAcruSAAvykCth0I74khgECI_n-kWjkuCgxifLT32I_8kW-reodokf9dOVi49BJJ-BbnQO3O7s7lNUCTEqIH-pb7xUjjwKgMn-Dmxt9fDMhq0P-CEN_5q16ZOJaYUBaMFoBSMlXNwyWAJR_EiCRfSdCrMcSot8KPgAssDPxgmFG6EhAnOt2hxNJXT03eP5YI3JhOGhQS-Zt1AU_fuq1gmdJVZw6X29ojOQ"}], "types": ["park", "point_of_interest", "establishment"], "reference": "CmRRAAAA_tjc1i4BFUc1XouZYy7Lj2iuAJdRZoJJMmeoohx2_zf8xhirVdTsWeHuWXS6oHURA4ZjXk4L0HuDexWyDbUMNMi4iBuuLSPt4Jq61JXRYDjiudwMKVEyahWZ7JC9v22iEhBpbc9eEQyUDiZ_23jDUmVwGhQJfvRGuryZxo4zqkTdsMvo7WOnFw", "name": "Willow Waterhole Greenspace", "rating": 4.3, "id": "0127506e8071350c2d48f0ca56e939045297a0f4", "job_title": "American-Midstream-GP-LLC", "place_id": "ChIJR6_2zTzqQIYRsA7wExgfDWs", "address": "S Willow Dr, Houston, TX 77035, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.4003322, 29.7388505], "type": "Point"}, "properties": {"photos": [{"width": 1136, "height": 640, "html_attributions": ["<a href=\"https://maps.google.com/maps/contrib/117056878997299689379/photos\">Marisol Brown</a>"], "photo_reference": "CoQBdwAAAMLvga4a7jl86W_lc5PyeOt9mZrdhguMzVYya6J8qFaG7_oSlVQM_2SRQIvILCbR_-JIlbmuFVVujtVTKePOrJniwAvvvG4W_HvJos9JtLcOklZPvbudK3Zn2yX1KCmiB9IlHuRBjjTortIN9F9Z1pOXklJnedMxvRxdSl1jybs_EhDYNVEgYbuqqZxuoQZVbRpYGhSGoRNcpXEBVzlYsd3HwwebFpwoMA"}], "types": ["point_of_interest", "establishment"], "reference": "CmRRAAAAEsq3fBZcfewyc5kipoAzrvb5VHlN7RuX2yNQUMWp9PE_dV755SIlux-bP52s46vXx0KA4Rz-l0xCgEx696wjF4Q8Y6L-vBpiCJjaa9uTTzNZJcPrB7Z-ClX4B6rROrcmEhCHdrJ92Lg2HdtUu2pq2_t5GhQRM9S-t3O_AnukUfPxZOewq0905A", "name": "Masters Fine Art Conservation", "rating": 5, "id": "a462c2eef4e22ea319485ae7b84f3d20756cbdd1", "job_title": "American-Midstream-GP-LLC", "place_id": "ChIJp8u2bZvAQIYRbosnWz6cVmY", "address": "1612 W Alabama St, Houston, TX 77006, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.3876169, 29.794149], "type": "Point"}, "properties": {"photos": [], "types": ["art_gallery", "point_of_interest", "establishment"], "reference": "CmRRAAAA4odAz-BdjrNBT5IoL_1iIH86fzRqpg1oa54598zowX90BDj2yrDOQNHUZAbTebdaxFMpqG7azDqZIOTb5JwK9-sye1WG2q46USQWLm0ELtNM0WJkr5yWELs0TD2bMoVfEhDlru8JX0ZbnszYLgGlAQ4CGhRfs-GtuDWuBgRjdK0i3HKTzaVx-A", "name": "Whitten & Proctor Fine Art Conservation", "rating": "NA", "id": "883a8c5ef35ab28e1630235ad65a6b16506a67fa", "job_title": "American-Midstream-GP-LLC", "place_id": "ChIJ8YuXE6K4QIYRn1SF1hazFEw", "address": "1236 Studewood St, Houston, TX 77008, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.3858767, 29.7300997], "type": "Point"}, "properties": {"photos": [], "types": ["point_of_interest", "establishment"], "reference": "CmRSAAAAuDsce0_DEtCLRlUFczghva82zJqDfqzQXrsTcZXIJNQz6AwU38m-vlla42QiP8fmBYpPlHf7TDcAifMIJaYGeq-YawqYG1dpfBhxIdIQ-cj4ubesFnB1eFlqOW3PlONCEhCkDZSgkgbyjwjj5uz2y4hSGhTY1zc64Oh7T7gMRmzh0-vxFwiLfw", "name": "St Mark Fine Arts Conservation", "rating": 5, "id": "ea2d4bac6d74716b33f456dff3aae0cc0b43cca3", "job_title": "American-Midstream-GP-LLC", "place_id": "ChIJKbDEoXm_QIYRcRFBlp0dE8A", "address": "4901 Main St, Houston, TX 77002, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.483218, 29.7482286], "type": "Point"}, "properties": {"photos": [], "types": ["point_of_interest", "establishment"], "reference": "CmRRAAAAHid9UssZiAdlZYOWL9NKx34U7kQZCJnHnJ_5SKklJHKj1eOiLWk3GMrhGkcbXBeiOo9oAKXdC727AvhwcVZuz439X-jHIABdos6R3AjsX1cBcBGMKAiEYh7wkLP3pybPEhCTnY1a2jKjM4J5yk2BRDbcGhTg6mStZIUX8qMg4ObN2ZWPZvFl2Q", "name": "The Nature Conservancy", "rating": "NA", "id": "90af6fb9fb926dde9f7103577cebc4150bbb1dec", "job_title": "American-Midstream-GP-LLC", "place_id": "ChIJq-m4EX3AQIYRJkn4Lhccp2E", "address": "1800 Augusta Dr #240, Houston, TX 77057, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.42318089999999, 29.7345943], "type": "Point"}, "properties": {"photos": [{"width": 750, "height": 437, "html_attributions": ["<a href=\"https://maps.google.com/maps/contrib/106788706324997826205/photos\">Erika</a>"], "photo_reference": "CoQBdwAAAEybZE1woo3iUwsm5PogeFMvyqLGWLylFuHF7OpP9izcRWgooHnMkw9wTjpAo2Bp-hK7qK7ZpfvRLZ8_gy5dBoIs491FhggELHNdljyOq-kWlgXg9MFaEsedZMyXH3mw2es27CcGyPRJvDM_4fw0O-9NC1UIGKnVwgXpxPxO_ImCEhDXbY-7qywK6AY26P6zLNigGhQhQZnOGXhFNySH88-DAjjVsuTDEA"}], "types": ["point_of_interest", "establishment"], "reference": "CmRRAAAAPEceV1dvFr-OIXMQhZ1xTJTnIwRSXG6-f-_aMMUIN45ZGBBhXcFGOBKk1fgu52s5IgT1JWuFW9rNdqT24nRDiQ1XphF3cNhanR1XgNpdU53xwqbAnzr9FAZrw9B_yJ8mEhBVpgxUadVv560jguzGZRk6GhRvA5B_dempjda6oVHV5CLd13qA-Q", "name": "Student Conservation Association", "rating": "NA", "id": "1c5ea7722fc0d99e9f7dfca55f5d9078224d51d3", "job_title": "American-Midstream-GP-LLC", "place_id": "ChIJQcqBXfDAQIYRErawO-goGj4", "address": "2990 Richmond Ave Suite #400, Houston, TX 77098, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-96.038102, 30.055621], "type": "Point"}, "properties": {"photos": [{"width": 984, "height": 985, "html_attributions": ["<a href=\"https://maps.google.com/maps/contrib/110279808588468038448/photos\">Peckerwood Garden Conservation Foundation</a>"], "photo_reference": "CoQBdwAAADhxLusnUgWAEKfTBLHTgCfMy7MgMcdUlsGmQUT0IRolWqTGNVa_CUROTWM5bI-zW3ou-jYkvrhwtD79p_cQtWwkQpuVZ9sxGauZYz7Tpi5zJKgprJRg51v1hgOScqJNyhWLcThWgKrxpdt_EX6fS4wHMgjZtg_AD93H9CFTr8VkEhAOXAk7gaJV5U-o928v1c8yGhQszIfTEIq1ZSv9Dm6VpDa2BdoQ7w"}], "types": ["park", "point_of_interest", "establishment"], "reference": "CmRRAAAAqYvHzrVZXglOw08Oyjrx8l821qwYIRee0hFmf7R5Qih7sQRh8_xVwSB1nQOmcvlevI_k7JMK9sU20qkr5BGVernoqdZ4ekYn2NIB2o8FgWhZDSt5b-IaPUgKJfMcOe6nEhBXZ3J8IkuqkV1uFO6sZEjTGhRDsDuwGw1_bSgt5a0EHk1seZHvJg", "name": "Peckerwood Garden Conservation Foundation", "rating": "NA", "id": "e618a4c618cd67ce4f5fdc165f640220ab3b53b2", "job_title": "American-Midstream-GP-LLC", "place_id": "ChIJmUR7pvHKRoYRIIl0o73bPGE", "address": "20559 Fm 359 Rd, Pine Island, TX 77445, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.64386449999999, 29.7515036], "type": "Point"}, "properties": {"photos": [], "types": ["point_of_interest", "establishment"], "reference": "CmRRAAAA4VJcV2fIM8dwq_dVUbX8aDKD9NwjrOVag2d293Xwx0lakkyTJ4TNkHSU6AzCAEni5TXStzIClqZQ9cm7nWclhdFzCOv6hmmru9cmDt28nIN07-20cccxGKdmoDliUpadEhA5HbwGUUfJJ3jApB7LmGUTGhQVJMs--cT_xAj-OnNTtNyd9J4f8A", "name": "H2O Conservation Technology", "rating": "NA", "id": "30c07988ef8dfc62dac712b9d587daa4a36f2539", "job_title": "American-Midstream-GP-LLC", "place_id": "ChIJIWZRKeHKQIYRXxta3wOMGGc", "address": "1725 Hwy 6, Houston, TX 77077, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.5705632, 29.7714443], "type": "Point"}, "properties": {"photos": [{"width": 3024, "height": 4032, "html_attributions": ["<a href=\"https://maps.google.com/maps/contrib/108143329814504597326/photos\">State from Jake farm</a>"], "photo_reference": "CoQBdwAAAG3FxjMUVxU7sMXn-spERgneSBPOWFBOlX4WaAeFXzPxgqIYAPw3_O3JPh65eRLUWgAu8pa6siFSivsJgxXCnZfp53wpSPz9Skrb-b3agWlv1gzdCYzvXxPSNTp-IjCsIfh_n666DDolb4xfTtYaQfPIPrXkARzXveHVwO7I5bgTEhDwWnkgn41-hErNcFhVKRjeGhT776Fq0pal9oeQb3tM1-YAnjAOKw"}], "types": ["park", "point_of_interest", "establishment"], "reference": "CmRSAAAASlMSsrj9ZAvkK0nXeh9_tR3RMDyaDlWerlXGwCdCaURxf3dTtoZWc6aGgyLmK5yLfr-Gx-rCK72yr-6VAw6D62GK3JrFdO3u7cHV33gLD9kVdPgeGaBlIjqTD2dlvF_xEhCvhC5Y_AsYjT9UkPyaQC5MGhQyRUYSh5Ro0PuiRV6x3doDwADEfg", "name": "Houston Audubon Society", "rating": 5, "id": "050a5458d86bdd1cee7b09678bd6256d0a20a73e", "job_title": "American-Midstream-GP-LLC", "place_id": "ChIJlQOxwVDbQIYR2uX_TZl0TYc", "address": "440 Wilchester Blvd, Houston, TX 77079, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.56820189999999, 29.770778], "type": "Point"}, "properties": {"photos": [{"width": 1800, "height": 1200, "html_attributions": ["<a href=\"https://maps.google.com/maps/contrib/108765250995932379967/photos\">Audubon Docent Guild</a>"], "photo_reference": "CoQBdwAAAOF-qtmu9gmWghdmK6pyRps-adn-ZIIEcIbn5cCbZir4nAIuzvyPKg3nOuiz15NIBNS1JEHaupf2bC-Lw5NXoimR1Qi6xvsvxndDiw2aPk4gnLFCRExMMFhTF9TYgUT_LrZZla645uci_y660LeutV-yC_WOppbgtXQ5ow1hm5KSEhBNXJi6am35D_nvwC5T3B3WGhToIY1pmkZnrIXTJZXiGYde-hV1NA"}], "types": ["park", "point_of_interest", "establishment"], "reference": "CmRSAAAAm1rk2KoQmp_qKlbFQgSSacKZQhqZrFMMBVCsVHtmA4Pb0D6y9xMdwyy9yTHdhbJrelBXFEssOGoRsYGNtOq0FsZgY09xXvZTIs3iMb0wy2oH29NR8r3gxii_jl9gEGTGEhCLoiDcyWJFLpTRgs9Mm4ZzGhSScUpuhriQgo4Y9g4eUrjB1Sr-XA", "name": "Audubon Docent Guild", "rating": 5, "id": "7ddd5daf76cc4979e2ba6b062322d1c77d5d1c07", "job_title": "American-Midstream-GP-LLC", "place_id": "ChIJI9XyNFHbQIYRtwHb8EtTpeU", "address": "440 Wilchester Blvd, Houston, TX 77079, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.44932349999999, 29.7803218], "type": "Point"}, "properties": {"photos": [], "types": ["point_of_interest", "establishment"], "reference": "CmRSAAAAnsNe2wnHH6cF6g9lfo4QFBExqS5rK9_2UqzMnPx16zUw-IemUANf0kBx9VgPqmNpQ2L76umxWK_18Ukez5oS-LcfxQ019ZHR6MiPfXnnIfongD2TPaiWCxIaMibWFVxOEhDXOdySWTbhgA94a6gx7tfzGhRLt8lFp1ggrNROPSdx4zHdva-Azw", "name": "Coastal Conservation Association-Tx", "rating": 3, "id": "7258b034e119f31e82320bca6e72781ee9f79d75", "job_title": "Procare-Therapy-2", "place_id": "ChIJcekacM_GQIYRPzL13cgQrPk", "address": "6919 Portwest Dr #100, Houston, TX 77024, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.47039, 29.655454], "type": "Point"}, "properties": {"photos": [{"width": 5312, "height": 2988, "html_attributions": ["<a href=\"https://maps.google.com/maps/contrib/101184977609161362375/photos\">aug4</a>"], "photo_reference": "CoQBdwAAADGzLaBDEP9Vd-djeCzhGNPRWuml39KlM3wqcapEp1S7I11leSnw828xt5ulke3B9M0N-kvLpqHcZ1TcCYLvHe8zVanV-mYGHEIy-x2ynibgOG-PzSEfTuDXop3TasRFtN09qVPajdZgGDmJnMxDFp0xZV70TZJLLdDxxaPpqoxiEhBC5ADdv--UPITDQS_MeZkrGhTBxzTPBlTGJ7jlGk-bZ81ILn5JLA"}], "types": ["park", "point_of_interest", "establishment"], "reference": "CmRRAAAA--CtnieXaGQah2L9NFDOWJiPLr09SEutTae4JSRiWn1zUrkCfXPLiLA4jYrOPsJXzYOmOFNkBT4nmibpwY7emOAvt1Y1PPV1zKYrUoSavkIDA-1xLvqozISdeWJ1eHEcEhBUt360dWkkiQdrUKyrBquTGhTTOxmeWeK_EHJ45UnJE8nQhWu7Xg", "name": "Willow Waterhole Greenspace", "rating": 4.3, "id": "0127506e8071350c2d48f0ca56e939045297a0f4", "job_title": "Procare-Therapy-2", "place_id": "ChIJR6_2zTzqQIYRsA7wExgfDWs", "address": "S Willow Dr, Houston, TX 77035, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.4003322, 29.7388505], "type": "Point"}, "properties": {"photos": [{"width": 1136, "height": 640, "html_attributions": ["<a href=\"https://maps.google.com/maps/contrib/117056878997299689379/photos\">Marisol Brown</a>"], "photo_reference": "CoQBdwAAAFF91kvCugZlwI3wn4ZZElJGPG7W3DbyZMRCw7z3cFDHg2pQFQbrQi6W7bd4HCTnVQU_GO6NWELqUi7umdsmW-4xba6I7i68QhDmvZqDO_YliZJuRwlhDoG_kFn5o8_rEPa_bqi0z3qfWYgkV-_d-wBOJ8mSHerPXERmf0UvxKVWEhBeS1g_hCE9RZy2XoDpqDnfGhRiJvQsaD6bZGEcEwG9879b1bARzg"}], "types": ["point_of_interest", "establishment"], "reference": "CmRRAAAAdSDKq0LeBo1ptc789_wTNFDzS2xfBts8l6hOvSbWr--eG4mNZlsimCU0Xe4pJ2pjRp8ss1xjTiHls6NTXO9tDkiCBMXcVbKEszHc1i6NXC1W9ZVdE38eyzAYk6YXIegDEhADPIgCIcsdpaS_L4H8IdpsGhQmxiQ8PgXSevhiAqbKQ5NgzMRRcg", "name": "Masters Fine Art Conservation", "rating": 5, "id": "a462c2eef4e22ea319485ae7b84f3d20756cbdd1", "job_title": "Procare-Therapy-2", "place_id": "ChIJp8u2bZvAQIYRbosnWz6cVmY", "address": "1612 W Alabama St, Houston, TX 77006, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.3876169, 29.794149], "type": "Point"}, "properties": {"photos": [], "types": ["art_gallery", "point_of_interest", "establishment"], "reference": "CmRRAAAA-gdwzGSph_bswky53mNwX2ZoBFxmkgNZagWzIi1gG-mNR3foOMpKsJlEujM5PyjUVznq1LLCXvPEwYa9AMoONYNOoOmyLgpXmZPbpxnd3P8MSGKkRaLGSJ3HKUIBgLbwEhAdpyrg4C0gG-Rdi3A_pPcPGhTlGi8ggdtC4-UMC0KdAfxbWfOk1Q", "name": "Whitten & Proctor Fine Art Conservation", "rating": "NA", "id": "883a8c5ef35ab28e1630235ad65a6b16506a67fa", "job_title": "Procare-Therapy-2", "place_id": "ChIJ8YuXE6K4QIYRn1SF1hazFEw", "address": "1236 Studewood St, Houston, TX 77008, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.3858767, 29.7300997], "type": "Point"}, "properties": {"photos": [], "types": ["point_of_interest", "establishment"], "reference": "CmRSAAAAANL6w0Uc_kUB2OSc9kR82yzzHywVFnvLMSivjF-uHJnfTj8jIQWjAxEOBX9hvUmmElOKZfeuCC7QAQcq7SN3MYlh_VzmGNhqWyfPW_kK2hk4XvGpAKikMbJeZ3UJ0s2_EhAFQCYNwS9pLalBkR5LC5H2GhRikGWTp6OJmL6okhtx7exgQUELwg", "name": "St Mark Fine Arts Conservation", "rating": 5, "id": "ea2d4bac6d74716b33f456dff3aae0cc0b43cca3", "job_title": "Procare-Therapy-2", "place_id": "ChIJKbDEoXm_QIYRcRFBlp0dE8A", "address": "4901 Main St, Houston, TX 77002, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.483218, 29.7482286], "type": "Point"}, "properties": {"photos": [], "types": ["point_of_interest", "establishment"], "reference": "CmRRAAAApyRHcyHlRjuKLtMmAwUcuCfRqrsPt5pLxQ4GfiqluJHjMRbTfneh7gt8v3goTXaTZCN3kn223oVw6VPk0PcxnmtjwDJ1_AocwJk7zvzb-FDgL2RXuscvt4UyYVjbL2PUEhD2JX5y_v14NJ90qLu6eOCXGhR0kVNEp_h7JZwt9-bmREXPkxvvVw", "name": "The Nature Conservancy", "rating": "NA", "id": "90af6fb9fb926dde9f7103577cebc4150bbb1dec", "job_title": "Procare-Therapy-2", "place_id": "ChIJq-m4EX3AQIYRJkn4Lhccp2E", "address": "1800 Augusta Dr #240, Houston, TX 77057, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.42318089999999, 29.7345943], "type": "Point"}, "properties": {"photos": [{"width": 750, "height": 437, "html_attributions": ["<a href=\"https://maps.google.com/maps/contrib/106788706324997826205/photos\">Erika</a>"], "photo_reference": "CoQBdwAAAP4wdCt3Ull43TwBZ_2raXCUJpSF6gYwAJVpeTkkjAOH6HqleDFu_SrzBKJ9cT2Hon8xCMGZFL5Lbp-YHNSwYBKjgyVTDA_SPd9j1W9noZT73kgqdeocR1IB0nFhR4rZvaCDAwMD8PMLTMjSA3oLeh7Jyv6iFzWTL1QyI-DPqKRxEhAbhV8NQPSwXBcTzT8vLjUkGhQmf6mqC3MJwBF06OlpIlKuIa9YTA"}], "types": ["point_of_interest", "establishment"], "reference": "CmRRAAAAVHzBDD_aZDoxW8I7Jhy6kjiBV-Jpn56fvruwglCQkcB_JKswFUK2r23f8kjNWMnBXXLf0QL47fX8sxqJN7Mn_N1gybX77-bOMx_BnzFLXmOrUUQMOeQuvURvKqJc_DaxEhBLPuug5AtynAOgQAgsBSlTGhR_a6YzlAjFAdxYZYJeZTCeKxXhFQ", "name": "Student Conservation Association", "rating": "NA", "id": "1c5ea7722fc0d99e9f7dfca55f5d9078224d51d3", "job_title": "Procare-Therapy-2", "place_id": "ChIJQcqBXfDAQIYRErawO-goGj4", "address": "2990 Richmond Ave Suite #400, Houston, TX 77098, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-96.038102, 30.055621], "type": "Point"}, "properties": {"photos": [{"width": 984, "height": 985, "html_attributions": ["<a href=\"https://maps.google.com/maps/contrib/110279808588468038448/photos\">Peckerwood Garden Conservation Foundation</a>"], "photo_reference": "CoQBdwAAAMppyd5biw_sMZ9-rq5nBYlLT4yy9wbCj9cA_sFM676WJaJOzuPCitzcTOJhoo-m2dcRRqe8scvtCaZvs5TKkzFF6HOjJAmT1HGx89yOvbuEbVIwf7FNzNjbqWLkqLOkCrZkRp9mOcHeLzmmMG7HzFY3y5Oaeg7hb7F9Mq-GA6_SEhB010s3DVNnmaj5sf7L127fGhSyWjmuLGMJU4UfevlI8bbzX23oPg"}], "types": ["park", "point_of_interest", "establishment"], "reference": "CmRRAAAAjZ2CsZM0bxn2DzD1Zeq9u4CwTwbjtfQoZ1HBVel0ZGLoDrivo5frzZMTJEPXI6kgSXVtJESydzX_9WOkJ5hiNc4vPeXLXtqzgDxkCiGsolI42Bzn9Lr-Ha_iSI1p-tz4EhAAAsMfMGsxvbpr44r3jm6BGhTz0kOotY8QP2gu6JQjjCFK9XL6jw", "name": "Peckerwood Garden Conservation Foundation", "rating": "NA", "id": "e618a4c618cd67ce4f5fdc165f640220ab3b53b2", "job_title": "Procare-Therapy-2", "place_id": "ChIJmUR7pvHKRoYRIIl0o73bPGE", "address": "20559 Fm 359 Rd, Pine Island, TX 77445, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.64386449999999, 29.7515036], "type": "Point"}, "properties": {"photos": [], "types": ["point_of_interest", "establishment"], "reference": "CmRRAAAA7Iud3_7j9lKLh3Q-LUO5mAEq-cLn1H097rF3J6Zx09KGsKRQmDhTYiZJQsa_wshIajNNcmc_yGNymg1D0rHqtgxTLeCMMr6FFCBNdLy-udFeViI-Pmq5T_Jq7rQ4lKmGEhAF9mYFsx25YiMZ_6oxOfh_GhSSMno-8DBagr1UNuAW93sa4kOCdQ", "name": "H2O Conservation Technology", "rating": "NA", "id": "30c07988ef8dfc62dac712b9d587daa4a36f2539", "job_title": "Procare-Therapy-2", "place_id": "ChIJIWZRKeHKQIYRXxta3wOMGGc", "address": "1725 Hwy 6, Houston, TX 77077, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.5705632, 29.7714443], "type": "Point"}, "properties": {"photos": [{"width": 3024, "height": 4032, "html_attributions": ["<a href=\"https://maps.google.com/maps/contrib/108143329814504597326/photos\">State from Jake farm</a>"], "photo_reference": "CoQBdwAAAMaRUwSTjVHHxC7RFjbdUMI-XkFxTFdDDiwfjVnbo8qObSVa2qAPEaYK10_Zq-kw5jCT7sAI9ci9ctaevNu3wah3o-gVw3iLKZxsXE0PpuANctSbum-PVj2um3Myq1WsS4tNCplBKgzXIknhl_v7a9bw_aUE_X-f6ZUT6OcRJ0YOEhCCtUk_YJiwZvufGBoyX0FzGhTpBAmofvgqh--kWKa3J7yvd4cuiw"}], "types": ["park", "point_of_interest", "establishment"], "reference": "CmRSAAAAXJ12LoTlgWY_aotOb059m9-vEgGmC_SOrdfPk6tyhQAGDERH7sv32OG5fQ0LhCIubCCMalhpmvhE3kRkjNERqc3aVHjjuZ2QULux8bDTeYDwFza5048_Emviu3Gp30pcEhCDOaj9xA1DSXbK-GcLfJnHGhQRzYSMjrBayVvowfFmJah1thhIrg", "name": "Houston Audubon Society", "rating": 5, "id": "050a5458d86bdd1cee7b09678bd6256d0a20a73e", "job_title": "Procare-Therapy-2", "place_id": "ChIJlQOxwVDbQIYR2uX_TZl0TYc", "address": "440 Wilchester Blvd, Houston, TX 77079, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.56820189999999, 29.770778], "type": "Point"}, "properties": {"photos": [{"width": 1800, "height": 1200, "html_attributions": ["<a href=\"https://maps.google.com/maps/contrib/108765250995932379967/photos\">Audubon Docent Guild</a>"], "photo_reference": "CoQBdwAAAPi8fa7hGQOKvF9cuHPMofjucsjDOS0G2dgD6ytj0Yuzyozi-7ywx_turr6ECMtnjDYwKJkyEwKNXv0__rcdx6y14TvFHE6UnOd46CmKt8hb4t3bL6e7W06uEImqQ4oeIe8ewyPt38mFMNbAwQSsi4d-LJsF3mMpPPAfWo2z5Yw8EhBFyRpniNAVh3S8S3hAaK8TGhQxCNbQ0H-_iDabx3NI_y9mjNyQBQ"}], "types": ["park", "point_of_interest", "establishment"], "reference": "CmRSAAAAZjuWJ3Y4FsnrJ_ZZ9bucI5aMmzocCGHH7HLOxNDMj7XJ9xIf7XT_e0QA9DVU37QlhlNfhVVu8HCkAAs9s8ReFb1CkBAjrRYyh0AJpaqjfP9UVvHN7u4qAg00N1gC2JwBEhC9VM1HKX2vm_ByZ7bb0mmlGhQSx0V0FFJ_h-3rRPnZHhBIi1t4rA", "name": "Audubon Docent Guild", "rating": 5, "id": "7ddd5daf76cc4979e2ba6b062322d1c77d5d1c07", "job_title": "Procare-Therapy-2", "place_id": "ChIJI9XyNFHbQIYRtwHb8EtTpeU", "address": "440 Wilchester Blvd, Houston, TX 77079, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.44932349999999, 29.7803218], "type": "Point"}, "properties": {"photos": [], "types": ["point_of_interest", "establishment"], "reference": "CmRSAAAAeerQSSx9PcsKNmK_yHDbKrie2SEJDiGSuSopBR7gZFJqwUwqgkEh0RvfB_wOoLi1sJHmBwmEM9O9lVNAdtEPJ-pwZJ7kMZJEutzRHIBLOqvIWHZt7YY_jXLBwJ_H-JQkEhB75Wp0H4uLy3MfAyWQJzUdGhRh_q1w8s_ZknP5sZCSN1ij5JZF1Q", "name": "Coastal Conservation Association-Tx", "rating": 3, "id": "7258b034e119f31e82320bca6e72781ee9f79d75", "job_title": "Pbk-Architects", "place_id": "ChIJcekacM_GQIYRPzL13cgQrPk", "address": "6919 Portwest Dr #100, Houston, TX 77024, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.47039, 29.655454], "type": "Point"}, "properties": {"photos": [{"width": 5312, "height": 2988, "html_attributions": ["<a href=\"https://maps.google.com/maps/contrib/101184977609161362375/photos\">aug4</a>"], "photo_reference": "CoQBdwAAAAy5TORj0hdxBxlCrOHyn7Mdkf4F_0z1Bw4qIMuhoh3oLN_nGt0y8XzZjtD3NERJXXviMBEs068joS70HSLNH8OmkVEMczbE00PTLVmajTmFqZIX8LihTUUmmO6Usurf2V7aMMZyWClB5ITG6uJ76Wg72-XflFZB3IRAVEMBvgIIEhAn2vZF7m8FndY93ZNEuycMGhSFomsBkUiF08yeUgKFJW1yVX5nqA"}], "types": ["park", "point_of_interest", "establishment"], "reference": "CmRRAAAAycBu7ecW3Xk5ljY_NSb5DRDnDb_BEJKv5diaG3fswMhtvUPeU0TffzH9va43-2a63UYCm8ecuYXRQSzMV6DJ1e0LOF--942NWTXbCD05BFtgfnDEgATVWJsHHQuue_MKEhD67f9FHRVqRdcyvXjbWjJSGhQA0M2yVitJgOEsZaPcIgJyTRmdSA", "name": "Willow Waterhole Greenspace", "rating": 4.3, "id": "0127506e8071350c2d48f0ca56e939045297a0f4", "job_title": "Pbk-Architects", "place_id": "ChIJR6_2zTzqQIYRsA7wExgfDWs", "address": "S Willow Dr, Houston, TX 77035, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.4003322, 29.7388505], "type": "Point"}, "properties": {"photos": [{"width": 1136, "height": 640, "html_attributions": ["<a href=\"https://maps.google.com/maps/contrib/117056878997299689379/photos\">Marisol Brown</a>"], "photo_reference": "CoQBdwAAAJBabwz2uteBOpclY-4EZa8AJUaPHDecraUpJ4I5rSuCpPr4MT7Bn9K36AuJ7let-mlZ9om-zb1PMEjfZZqbs8o6pNJbmJ8PXydvYNBpnqyciZzOMIQsNSO5WcLV2HJONklbwUTHdlZG_QnQKF76wbnW3zVWdzvbNKwrTD46Vo-dEhBlIsE27iBNq4EJKlwQeXDwGhQSVVtfTSs2xtxNaLRyiD5uKevmbQ"}], "types": ["point_of_interest", "establishment"], "reference": "CmRRAAAApJ_aq7TxaOSJ5ETvO0OvZhmxWUCSmgYVqAnRAPTJqXoS3Wp4xRcuDk_XBnCms54i-eEdZIPAw8J_8fa0E2itzlI8Tr9smdjAtkwz831-QzkKizrQNOrD2LKyaTFkKqfJEhAHrpI_yDSUQ30vET45Lri2GhTE3JIlxYuL4kkG8xVDj7L4Xp1Klw", "name": "Masters Fine Art Conservation", "rating": 5, "id": "a462c2eef4e22ea319485ae7b84f3d20756cbdd1", "job_title": "Pbk-Architects", "place_id": "ChIJp8u2bZvAQIYRbosnWz6cVmY", "address": "1612 W Alabama St, Houston, TX 77006, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.3876169, 29.794149], "type": "Point"}, "properties": {"photos": [], "types": ["art_gallery", "point_of_interest", "establishment"], "reference": "CmRRAAAAZRIIRDzN4tH6R5mHKBG9T_bvMGP-TCSln255WdHpqGDvJI6JdGPNEcYblXPtCkSY2fOXxG4l_n31QM1ED-B-wRhz1d-9cbDQEETmZa6VCdLOYEILWwcM9GcH3FCNR2_nEhBLUjYrOVIUFrgAUrXoYnZgGhRXVS2TRvFkiwpYXv9rWXfCaAMfoQ", "name": "Whitten & Proctor Fine Art Conservation", "rating": "NA", "id": "883a8c5ef35ab28e1630235ad65a6b16506a67fa", "job_title": "Pbk-Architects", "place_id": "ChIJ8YuXE6K4QIYRn1SF1hazFEw", "address": "1236 Studewood St, Houston, TX 77008, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.3858767, 29.7300997], "type": "Point"}, "properties": {"photos": [], "types": ["point_of_interest", "establishment"], "reference": "CmRSAAAArzkfcjMN9OYMj1ke8RpG_mx204uk9XWKM3c4IysUmRBYvetyY0mjIwcTFM5bgtGAfkw_c5oC1K8Hacz1GQtIcghYjevnG0YE-RdHnVFULIOzCy8halcS5rO3z3i5FkWREhAaMXiFAiorNUqhzofc6Qy0GhRzZgMokZHGI0ML12FjkkPGKcJXDw", "name": "St Mark Fine Arts Conservation", "rating": 5, "id": "ea2d4bac6d74716b33f456dff3aae0cc0b43cca3", "job_title": "Pbk-Architects", "place_id": "ChIJKbDEoXm_QIYRcRFBlp0dE8A", "address": "4901 Main St, Houston, TX 77002, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.483218, 29.7482286], "type": "Point"}, "properties": {"photos": [], "types": ["point_of_interest", "establishment"], "reference": "CmRRAAAAqnUpgMsuR5U-PLOhSRj1Gv1Smr1JpmDBSm5yyOXNTiIMbkTCDPtZ9KjYXJc95F7vXHTVjVcDOmiz_3Ov7it9umduglqGtX1R9WM8VmLEtwxvaEZgJjpnU6UqAW9kK1XUEhA0Yie3EeslTcSkY8Vjq32fGhRHnm7YGIw9JNO_iGFf6hASIDQ7Zg", "name": "The Nature Conservancy", "rating": "NA", "id": "90af6fb9fb926dde9f7103577cebc4150bbb1dec", "job_title": "Pbk-Architects", "place_id": "ChIJq-m4EX3AQIYRJkn4Lhccp2E", "address": "1800 Augusta Dr #240, Houston, TX 77057, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.42318089999999, 29.7345943], "type": "Point"}, "properties": {"photos": [{"width": 750, "height": 437, "html_attributions": ["<a href=\"https://maps.google.com/maps/contrib/106788706324997826205/photos\">Erika</a>"], "photo_reference": "CoQBdwAAALMONDeWUDuLusYBB5da2ILRPXbwdPV5mlJ7znjKVuUdlprXkNVIhY7ZJi-hDWHnY8S-Au3bBYB3XueNtIX1KqdGGPZcKe3yST7n-2zrtlKV2-x8DbipnYUu7Cjet-K--JaqClgBGOM0OgVD_0hRdSeABZOPNx_SwMBQolRYYzH7EhClAQFb_KHeZ3QRacPHxiO-GhRKU5v17tB8S9YFa-ZzU2AM5TgveQ"}], "types": ["point_of_interest", "establishment"], "reference": "CmRRAAAAkn_x3ANZ4ZmLWvqDdqSggQyk9FpAdAaKBrWETAAbIhLSZBc2E9fS838DD6V6Gf4KrNKluYWPfyrdON9IInhqVMynDBGug830lbVp6HBq-SlzHQ16340-pLiltW2URWOYEhDOSmErvF-okwoVHdoGVHJSGhRG5AU3ZwrtquC1x1n59IKNFAjutw", "name": "Student Conservation Association", "rating": "NA", "id": "1c5ea7722fc0d99e9f7dfca55f5d9078224d51d3", "job_title": "Pbk-Architects", "place_id": "ChIJQcqBXfDAQIYRErawO-goGj4", "address": "2990 Richmond Ave Suite #400, Houston, TX 77098, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-96.038102, 30.055621], "type": "Point"}, "properties": {"photos": [{"width": 984, "height": 985, "html_attributions": ["<a href=\"https://maps.google.com/maps/contrib/110279808588468038448/photos\">Peckerwood Garden Conservation Foundation</a>"], "photo_reference": "CoQBdwAAAP1Ij_T9LLbHVwNLYGNoG5V1kOHQNoFVS5yNw00CiyzZtT4TLZjPQCwEs7kItUJYmnjisJ3Z5OEHp8uXnQdfFVqC-tz3YhBBYEIwK45S_nNngTKZeUEXcYsDNUh06bx-BIQ14pWJ-XJWOfvgBHPx4e2fV9N5AHEBj82zHkYYK6LyEhDgDmHKTj-wjj7UCKGorr-EGhR__OiQBnbzTqu0EZIQdQ1SCExZTA"}], "types": ["park", "point_of_interest", "establishment"], "reference": "CmRRAAAAoQQysaYmDVaEOxEK_GLBrxBECGOh50_xFTRPuPEm8KxRwnbBMGfXuePgVlA8zyei6ypA9WGBQr5lRndePlrSLt7XaQRPaWr9itpOGuISNOP1cmljFDNqr36rDDgAI0bBEhAyVLcTSM9fsfLR6S8_gyEYGhTjeZvtHQmX5q_O-Z9uEhfrM3VG4g", "name": "Peckerwood Garden Conservation Foundation", "rating": "NA", "id": "e618a4c618cd67ce4f5fdc165f640220ab3b53b2", "job_title": "Pbk-Architects", "place_id": "ChIJmUR7pvHKRoYRIIl0o73bPGE", "address": "20559 Fm 359 Rd, Pine Island, TX 77445, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.64386449999999, 29.7515036], "type": "Point"}, "properties": {"photos": [], "types": ["point_of_interest", "establishment"], "reference": "CmRRAAAAjMlHhzM9vScV_V89ImFEzuKCuEb6Pry7evqyt-RrFnx6ur__PEUCmHWsosviE7MR7aKqWxZZR30Di6E1Mgd2JgSwvrmqfgYufHa1dfSRXsUk8i_1De9kWf9rm-0CKzUlEhBILjpsH6doIcblroGJyDwpGhSXXDJvTZeqiqNaw48SHx6XAEPYmQ", "name": "H2O Conservation Technology", "rating": "NA", "id": "30c07988ef8dfc62dac712b9d587daa4a36f2539", "job_title": "Pbk-Architects", "place_id": "ChIJIWZRKeHKQIYRXxta3wOMGGc", "address": "1725 Hwy 6, Houston, TX 77077, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.5705632, 29.7714443], "type": "Point"}, "properties": {"photos": [{"width": 3024, "height": 4032, "html_attributions": ["<a href=\"https://maps.google.com/maps/contrib/108143329814504597326/photos\">State from Jake farm</a>"], "photo_reference": "CoQBdwAAAI8wldJgL4u9CBb0WsaZF5eLbzvWTV4_u-3ODSCsU7Yt5Jk1i6Ar4TCnv5rv9LArbMExv1LV-qOaj0K6cCES2ptZJpSTzKjEIA5quzWuR2yxSv5c1Tds1s0n6DBhSjUb-CSDiTBSSk9bdxT1cZ-wBkiFbx7YS4OlABAwXMQG5vR4EhDJuxMBvpyZx425g5Wd49o0GhRaverXHJ-ltU8qTfrIJdzw3lGIRA"}], "types": ["park", "point_of_interest", "establishment"], "reference": "CmRSAAAAgsYwiS41g9Shge3zXP3wixsv5tZX5xQoFuyrvqYI0Lxb6EwkscRn91knxrDDoW11eI9LBM2fONjEpWsABFoBi_Eiuu5XRs6gfXaC7K79GWjEZ-0ctE5LaCSmAFRAeH3pEhC0-3ZWDFWLA_lFcgOhb_ksGhT8q7RO5_29tP-wUlJ9ESwVZp46sA", "name": "Houston Audubon Society", "rating": 5, "id": "050a5458d86bdd1cee7b09678bd6256d0a20a73e", "job_title": "Pbk-Architects", "place_id": "ChIJlQOxwVDbQIYR2uX_TZl0TYc", "address": "440 Wilchester Blvd, Houston, TX 77079, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.56820189999999, 29.770778], "type": "Point"}, "properties": {"photos": [{"width": 1800, "height": 1200, "html_attributions": ["<a href=\"https://maps.google.com/maps/contrib/108765250995932379967/photos\">Audubon Docent Guild</a>"], "photo_reference": "CoQBdwAAAF8gxO5dPvdJESCByhYMQjjOxqwVR7wscD0uiGJrJF91S8IVsSh1mBEisClj5pLMcjQ_Y6SQdf29-ggPkVAKb6XIONJe_7w7Kto6MpPU1D1cAxGvpHXg4hVL407zkAEJ0BHvuHQtidX0M1SrS8mHMbPbbP_iCQN4hmMSVLlJty7oEhCUnQwycGKwyN8nWaCeCAHuGhRRIe8Dx8CN1JMXU_i7HhoINEAn8w"}], "types": ["park", "point_of_interest", "establishment"], "reference": "CmRSAAAAff3LHYSF8mQoqxdE0X_x5fvb0zvPs4QAtcTmpkosLwRfIMbbaS4xctA_yiW_s8jhYU3GNAzZPkogcfU-5N_sWO6gEAi1Ummz3aquUl83t04b4UcJ2aHpspD-lM1MW_SwEhCqma8glHtXczW_QA-Mbx0eGhTPauAEVMZUNGp9qHGX5VSQID8Tow", "name": "Audubon Docent Guild", "rating": 5, "id": "7ddd5daf76cc4979e2ba6b062322d1c77d5d1c07", "job_title": "Pbk-Architects", "place_id": "ChIJI9XyNFHbQIYRtwHb8EtTpeU", "address": "440 Wilchester Blvd, Houston, TX 77079, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.44932349999999, 29.7803218], "type": "Point"}, "properties": {"photos": [], "types": ["point_of_interest", "establishment"], "reference": "CmRSAAAAGFFTges8nOVyDmaNLcfH5ptf52nLDoUKYiVnOlW6y4zNYz4uQXb35qaQUKv7K6PR5qCnNu68AfpK7GCqLCPyvPeFXwkGTu7QBKUtLpBtlBV9ruVzw1X1D3wMkto7dN4hEhA7evFV0caMRzqZFu0hr6zYGhQoBf7LPkB7lI3pRXA4HKWjsGuxPw", "name": "Coastal Conservation Association-Tx", "rating": 3, "id": "7258b034e119f31e82320bca6e72781ee9f79d75", "job_title": "Southwest-Key-Programs", "place_id": "ChIJcekacM_GQIYRPzL13cgQrPk", "address": "6919 Portwest Dr #100, Houston, TX 77024, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.47039, 29.655454], "type": "Point"}, "properties": {"photos": [{"width": 5312, "height": 2988, "html_attributions": ["<a href=\"https://maps.google.com/maps/contrib/101184977609161362375/photos\">aug4</a>"], "photo_reference": "CoQBdwAAAAde9zRdNElxaXhXoDd2ibdnfsKJ_ImwzjFPeS0OXfcVqYBRBJCursmZAZ2a9BNhLesf34o_B43ysvvqRF_--rWyJ_EFxXEtPIIVc3OxIaIU9ugPvt734O7s-Ly5oxZRHqwwWgBtyJcAo05HQUWGvix6vDtjxSbHFmcO3eeRZDfaEhB4Mv8H8I68bRVywFUVDxKJGhTlPBuqWK5KRcSYC8u3S9PQSRTPvA"}], "types": ["park", "point_of_interest", "establishment"], "reference": "CmRRAAAAhscigUoOV9m3cVoQMoj2V1kdBBWlXPc8iqDxRRaKW06vydTQlVNt_ozH1bFAcmhXOsjcrE_6etsrdCK-3Q0E3IFP2-S3uoQ3JvcEi1nzb58gu_xDb7eJhrw0qWNt8gkIEhB27zEEZV3g6jNbgvtqLcd-GhS1RmzT5BDolQ18_vx55zkUo5-H-A", "name": "Willow Waterhole Greenspace", "rating": 4.3, "id": "0127506e8071350c2d48f0ca56e939045297a0f4", "job_title": "Southwest-Key-Programs", "place_id": "ChIJR6_2zTzqQIYRsA7wExgfDWs", "address": "S Willow Dr, Houston, TX 77035, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.4003322, 29.7388505], "type": "Point"}, "properties": {"photos": [{"width": 1136, "height": 640, "html_attributions": ["<a href=\"https://maps.google.com/maps/contrib/117056878997299689379/photos\">Marisol Brown</a>"], "photo_reference": "CoQBdwAAAAGMg2VNxvU61lmdIhyoCbGJWeKkgrBiTOwcO6Qs0uBDPJUrS3hlUAr3ksjPbyJMF5JF6JBg2udE4lCuEfaU6AfhlEoWJXK-FaNwujywZtvwmstdqp38xt-ENFb0nWiaxiZxmFHccAVdWko_qq0t83cuKt_nPM_pLL3r7vfzWRK4EhBpNfHfL9D1x1rEg-SrQPKnGhR3pbyco1sf7chg21PWhiZOzr5iAw"}], "types": ["point_of_interest", "establishment"], "reference": "CmRRAAAASUSB__sFmzPwSCPDZq8sYn_i0jIjsFxHA_fxstUf3FtDzOh7gwR2TFzr89VlKWxTGxMMPBRsvgGH3AQgTqCTbKPY5Bjq11Dly2cB-pQYgDp3KZllI2VdpMWoIdG0JeMYEhC0K5A0QeN7a1frjPNFNIcRGhSyV92W3DajCpKiuoBgXiFubMSU2A", "name": "Masters Fine Art Conservation", "rating": 5, "id": "a462c2eef4e22ea319485ae7b84f3d20756cbdd1", "job_title": "Southwest-Key-Programs", "place_id": "ChIJp8u2bZvAQIYRbosnWz6cVmY", "address": "1612 W Alabama St, Houston, TX 77006, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.3876169, 29.794149], "type": "Point"}, "properties": {"photos": [], "types": ["art_gallery", "point_of_interest", "establishment"], "reference": "CmRRAAAAggDeOXLIzOAVChFws3Wr7ntAjNscXNK7dkCPJsX9ub6JXFPJd963pYp9cpUCMps59vDx6ALIPqZf9DKaDHZW-f882dAoAAm21uY2AjESG8NLZziDM57eK05gVDlZ8mWSEhAnOWCinZtVIF-nTLQkCdU6GhRk3aHUwhXO-b6KsWN1fyKJNcgWEg", "name": "Whitten & Proctor Fine Art Conservation", "rating": "NA", "id": "883a8c5ef35ab28e1630235ad65a6b16506a67fa", "job_title": "Southwest-Key-Programs", "place_id": "ChIJ8YuXE6K4QIYRn1SF1hazFEw", "address": "1236 Studewood St, Houston, TX 77008, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.3858767, 29.7300997], "type": "Point"}, "properties": {"photos": [], "types": ["point_of_interest", "establishment"], "reference": "CmRSAAAAeeckwDwnxNU8lOvhECW6L50n9-DaVLo5vpvG0RlzYzXbGKg4d0yqEZV-C1v92LQQO9W3_b7KEMtm4qV96p-NHC2zjfU69cGsi6VariBvEhtWKdAS-aB0peA3uDtX0UkdEhAssJ6hf17Z5_GdWhcjGe6sGhTtIZcyFk5IUR1EkrrHrnwLBe3BLQ", "name": "St Mark Fine Arts Conservation", "rating": 5, "id": "ea2d4bac6d74716b33f456dff3aae0cc0b43cca3", "job_title": "Southwest-Key-Programs", "place_id": "ChIJKbDEoXm_QIYRcRFBlp0dE8A", "address": "4901 Main St, Houston, TX 77002, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.483218, 29.7482286], "type": "Point"}, "properties": {"photos": [], "types": ["point_of_interest", "establishment"], "reference": "CmRRAAAAvC74r3TcougIgUkY3fe-lgSaTBYGIgF4mNI9KnFmQoEdq1bZKL6fs_R0OyAUf2BFJjzQvvpGlZtjRHnvxVEtXTcBG7RBJ5RqgJ0_SGCmxjMnLPaJOxex9yFaqnA8TBSUEhBUtpRBQBqbRj-0dMohn3GIGhRKFjiAglR5iRk234hx6lIQQTOrPw", "name": "The Nature Conservancy", "rating": "NA", "id": "90af6fb9fb926dde9f7103577cebc4150bbb1dec", "job_title": "Southwest-Key-Programs", "place_id": "ChIJq-m4EX3AQIYRJkn4Lhccp2E", "address": "1800 Augusta Dr #240, Houston, TX 77057, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.42318089999999, 29.7345943], "type": "Point"}, "properties": {"photos": [{"width": 750, "height": 437, "html_attributions": ["<a href=\"https://maps.google.com/maps/contrib/106788706324997826205/photos\">Erika</a>"], "photo_reference": "CoQBdwAAAGI95uB6GKl4qaAkbsoi2Aj8nUHiYI1ld_cqmMrdLPtuaPNwNt1aSbiMP8Qv5CqHFts-DSURoeCZFIC27Oe7h5NuaPnvsgANATzeJBXJxNLl4I4aCZoWnxM45cZ3rcMLbBJKlkUuckIrZP2-NY-f2vkNWXlRGskPVM4cdQkHD5aAEhCSn9a-rjSDaZ7cl37A2xY-GhT7JUqvpJZBBBp6ZPiz0PMuomBi_w"}], "types": ["point_of_interest", "establishment"], "reference": "CmRRAAAAwRlxIi8FBkY3P2qCKvU-r6BB9XSQeF1LlDmhdWYYBpHIQ2_tZPqDBmbcshXnNNLkdUJhagfP3jMy0ELuOqt1YToZYAH_NCKrxoh18iNmWHsT2MxDJdfRlBqbR9wpokLxEhDHkvpGUyseTF78MQSQhbXlGhTi87APuhYDxfwPGKsUAlv6WdJzdw", "name": "Student Conservation Association", "rating": "NA", "id": "1c5ea7722fc0d99e9f7dfca55f5d9078224d51d3", "job_title": "Southwest-Key-Programs", "place_id": "ChIJQcqBXfDAQIYRErawO-goGj4", "address": "2990 Richmond Ave Suite #400, Houston, TX 77098, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-96.038102, 30.055621], "type": "Point"}, "properties": {"photos": [{"width": 984, "height": 985, "html_attributions": ["<a href=\"https://maps.google.com/maps/contrib/110279808588468038448/photos\">Peckerwood Garden Conservation Foundation</a>"], "photo_reference": "CoQBdwAAALuJ2T-ipI3tVIRs_y8LgcgG4pJaHB6jOvWM6Rq72rWB46j8Btn6ogxEmlQvPBhfnS0V4mZn0HO0jd6MA2FYhyDGQzD6C_fz8o2HqsCWNpOa-zJ8FV0Sj6U99T6ZbhXzFVlp1nKBs-SiVgOA7APTXF4s1MEp6oYBztvPh5v6cYkMEhALzMejKPTS4RxyGJK0x2m2GhSr-zIUHq0-zRRVaGXidufaYAWAeQ"}], "types": ["park", "point_of_interest", "establishment"], "reference": "CmRRAAAAdYryz4whJ-2Nu9SYNu2L66hkBXzlu_hZXhfKFFunzPJTyjSUrZK69D67KAbddFoPyCsrWWPpaDPO-iIPCmlkWV4QGnHDtQnOI4wBotlSJEyU7r2yHcxxTwikt3JqteK9EhC1hQGslQQVzJT4G5Mh0elgGhTvaCmRruzOhQgjeXQ8Xbnhltr9Gg", "name": "Peckerwood Garden Conservation Foundation", "rating": "NA", "id": "e618a4c618cd67ce4f5fdc165f640220ab3b53b2", "job_title": "Southwest-Key-Programs", "place_id": "ChIJmUR7pvHKRoYRIIl0o73bPGE", "address": "20559 Fm 359 Rd, Pine Island, TX 77445, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.64386449999999, 29.7515036], "type": "Point"}, "properties": {"photos": [], "types": ["point_of_interest", "establishment"], "reference": "CmRRAAAAtTx-KkJVarPnekkFhU4WI2-XpbAb8Hqv8X6XFCJI8of12O_EaXBLzE2I0V_yL8WffJjVwmtQD2GzZWcAz35Cp_ucSi1lqsSWZTuwhGxCHlcpiaIG_SJeiP0GIc1XuCALEhDVP7UkyyN_vCO7Y4Hx6UFhGhRA0hKxEIDDIEKyocUtiygUNNSjZw", "name": "H2O Conservation Technology", "rating": "NA", "id": "30c07988ef8dfc62dac712b9d587daa4a36f2539", "job_title": "Southwest-Key-Programs", "place_id": "ChIJIWZRKeHKQIYRXxta3wOMGGc", "address": "1725 Hwy 6, Houston, TX 77077, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.5705632, 29.7714443], "type": "Point"}, "properties": {"photos": [{"width": 3024, "height": 4032, "html_attributions": ["<a href=\"https://maps.google.com/maps/contrib/108143329814504597326/photos\">State from Jake farm</a>"], "photo_reference": "CoQBdwAAAOWYwcQuhobcTrE-N-VeYmTPXXt72BqgOnhIwRkDbuc-b9N_bx0UCCtCDtlh8D8b7JJYj-Fy9VtIlCZ1jO4rGAv5KqTByRctomA6gTctvzs6QePmbdTKdvrEdIJYwq_IKgg7NWGvD4rMqRyx3Q9MGT1XbhfSP-KUSdw_M6tUNs1pEhBXMwJSCFEVECRwQUDA3vB4GhR_dH7v_KqSF-0TqLrbqdDuGCZHbw"}], "types": ["park", "point_of_interest", "establishment"], "reference": "CmRSAAAArp51yhLkFh11Hq3ArFQ4XBTWm5cMmIP5cBMuktF745OHJIKRdSuKu3e8AzYw4sP-KxIoU53RYDybs0O7rHejzPmdS9Ar40JFtYttxlQu-opcaWoeSEUss0XQ_Q2Mot9bEhBJUhAh97SLqbt4qi3Kocu2GhRX5o-jV4H6Y40m_qb4jwijvBViww", "name": "Houston Audubon Society", "rating": 5, "id": "050a5458d86bdd1cee7b09678bd6256d0a20a73e", "job_title": "Southwest-Key-Programs", "place_id": "ChIJlQOxwVDbQIYR2uX_TZl0TYc", "address": "440 Wilchester Blvd, Houston, TX 77079, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.56820189999999, 29.770778], "type": "Point"}, "properties": {"photos": [{"width": 1800, "height": 1200, "html_attributions": ["<a href=\"https://maps.google.com/maps/contrib/108765250995932379967/photos\">Audubon Docent Guild</a>"], "photo_reference": "CoQBdwAAAAWdu5oErbRP5RtxRwqhh9Znb1FvCFuj50FaIAdYSD-Z8wd874yy8V6Sdykb5ZT6nQSWUL1CfvASknPfD-tMCO651mLrN_N9kd0kHmwyIMdwGs_OWpmGxRHWs6reGcXI0LRcpGews5R3p0n2s2LpshM8bAL8LHCabt5pHZLlySAnEhCJi5EN7_gm9gCDq-nDGKrEGhQeoxYzci3A01qJk61H8tGvI8K7Bg"}], "types": ["park", "point_of_interest", "establishment"], "reference": "CmRSAAAATKINx3qwl40wPnj5PbzgLOER0hM-mG3qfDhP6XRp1erelxmac-HEr7eWNcbU0lLkD9TSAWuWICOOtmAdsK89bqug0PdMbfSIVWPKdcjcUPGnO8Ol_vqqxf4awi8jutVoEhCoaryK44YQ0-gO8h6WPgyqGhS2nq-6Vv6GM1GeY6ZBTTjzg4ikGA", "name": "Audubon Docent Guild", "rating": 5, "id": "7ddd5daf76cc4979e2ba6b062322d1c77d5d1c07", "job_title": "Southwest-Key-Programs", "place_id": "ChIJI9XyNFHbQIYRtwHb8EtTpeU", "address": "440 Wilchester Blvd, Houston, TX 77079, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.44932349999999, 29.7803218], "type": "Point"}, "properties": {"photos": [], "types": ["point_of_interest", "establishment"], "reference": "CmRSAAAAub9UQymr2Bo1GrTGHhEX-jNARlE1-CzaQb8lIlU4yEYlNInpmIc3_s57JIzM-pGm5sMaXcSiy8RcSt1B_tY6FSR8ylWRyBXr1y-V1vz4wwdLXNsicHk-yTiPuYRgjJp_EhB_ay1aaJOyLnDSMMDazGvZGhQ18fhc7SHBBWrDNHws-emVu57dVQ", "name": "Coastal Conservation Association-Tx", "rating": 3, "id": "7258b034e119f31e82320bca6e72781ee9f79d75", "job_title": "Statoil-Gulf-Services-LLC", "place_id": "ChIJcekacM_GQIYRPzL13cgQrPk", "address": "6919 Portwest Dr #100, Houston, TX 77024, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.47039, 29.655454], "type": "Point"}, "properties": {"photos": [{"width": 5312, "height": 2988, "html_attributions": ["<a href=\"https://maps.google.com/maps/contrib/101184977609161362375/photos\">aug4</a>"], "photo_reference": "CoQBdwAAAFgKzfL0_viYwQchBB8jqXZeJjQ4qGAcPAYAgyuvpq7SlQuABJt9n8IxQH56V9jXb9EVBB3mnpXFf4XVOkH51YJB6QA-di-ww7VLjuPCwEIoLBe0nnKO1XwIuOARB9vH4eUQS-wa3uhQrM5yD80DVx-aWJLCR0Zhs59ErLtLIm9kEhDX7ZRS_h4J9tuvG_96ytLIGhSzn0gT9cCZ60r5qxZH9O3CkD9S1A"}], "types": ["park", "point_of_interest", "establishment"], "reference": "CmRRAAAAU40fv1F5LQXGvA6U4DuzKNRlJc3pB19Ic7aCY28SE9x3tnW3MUbpaKGlqeWBTowogaqd4tGAZltyF-AxcFUfYutD8JPneQX1frT-5Yql_tKl1FahSL_fblweUcYm60uGEhB1oumHTsUrw28Fw1x5rMwRGhRlfCvGph68hkpshAamDZ-n_AWF3A", "name": "Willow Waterhole Greenspace", "rating": 4.3, "id": "0127506e8071350c2d48f0ca56e939045297a0f4", "job_title": "Statoil-Gulf-Services-LLC", "place_id": "ChIJR6_2zTzqQIYRsA7wExgfDWs", "address": "S Willow Dr, Houston, TX 77035, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.4003322, 29.7388505], "type": "Point"}, "properties": {"photos": [{"width": 1136, "height": 640, "html_attributions": ["<a href=\"https://maps.google.com/maps/contrib/117056878997299689379/photos\">Marisol Brown</a>"], "photo_reference": "CoQBdwAAAIFAK-6cPcWR7zdHZ40DHj53ims2VBSrAjIU53H1YYCraxbHTiVKauHVoQvSnmNreUO0Ms1m9n8MkXDcV6YoY3tVxIPDTc9_CvmQ9d9wjez2XC-EecN4YkObSXDdFGKR-pt-Hj_1p7iIjAHDdI5MriX0uPKOmbe8bh4w829kt4DdEhBfY4O0Ves_XmX1rFxUJq6MGhTsCxdey4MkAeI7z_wYxxWXzmAdEg"}], "types": ["point_of_interest", "establishment"], "reference": "CmRRAAAAHM6W2FYvcoYnTaW6mkx9A_m3441chAjqLfgjipYVN-SgS_YjFCO4wWOFpoy2Mw5rfIpwOLsunkCgArjQkh9lkV_gyUFP_oq-mid9FG0cbG44lrScHx-cIsO8vQEQCro7EhAl7PECHesGqq8_5e1bXBG9GhQ3g-X1yvLZ2XARutQ0cK_STDXHJg", "name": "Masters Fine Art Conservation", "rating": 5, "id": "a462c2eef4e22ea319485ae7b84f3d20756cbdd1", "job_title": "Statoil-Gulf-Services-LLC", "place_id": "ChIJp8u2bZvAQIYRbosnWz6cVmY", "address": "1612 W Alabama St, Houston, TX 77006, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.3876169, 29.794149], "type": "Point"}, "properties": {"photos": [], "types": ["art_gallery", "point_of_interest", "establishment"], "reference": "CmRRAAAAtpnTUti6x4BT-H9Vyf3njiw_mu6YeC4q1ZZj2XvZm3nyJbJvs3ovgTBk6S2xDZKr6WcxE62pX9gRb7pV8Zdg7F-fL940H2_K--ubDw8_RiVivEu6eG95Ljdw1BPEYlqlEhDExMGI0LXN-y6NW0qGssmvGhSl1dNgbOq-RSPguKNtY-FquHUppA", "name": "Whitten & Proctor Fine Art Conservation", "rating": "NA", "id": "883a8c5ef35ab28e1630235ad65a6b16506a67fa", "job_title": "Statoil-Gulf-Services-LLC", "place_id": "ChIJ8YuXE6K4QIYRn1SF1hazFEw", "address": "1236 Studewood St, Houston, TX 77008, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.3858767, 29.7300997], "type": "Point"}, "properties": {"photos": [], "types": ["point_of_interest", "establishment"], "reference": "CmRSAAAA3DkA3McunLXHK4KoTZ5KS8S6v-zGM6QQ3_8C5ZPC9hcSdg99qdOuxYhkw9m6oz81ur4qO6lMk-LwyFIx0kuSZ50ZYSecfKc5ooxIdEKP2A8y0Ocki28G1VIOVcn7bR-FEhCuB5enbmOm41jnN75cxhQYGhSHE0al2GIEelrr026cI2xQXDaEOA", "name": "St Mark Fine Arts Conservation", "rating": 5, "id": "ea2d4bac6d74716b33f456dff3aae0cc0b43cca3", "job_title": "Statoil-Gulf-Services-LLC", "place_id": "ChIJKbDEoXm_QIYRcRFBlp0dE8A", "address": "4901 Main St, Houston, TX 77002, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.483218, 29.7482286], "type": "Point"}, "properties": {"photos": [], "types": ["point_of_interest", "establishment"], "reference": "CmRRAAAAlVIKH1372aurdScb8vvatao_d4YrY015ruseNpJCJsSUMHN9bXbFKBbaj242RkRL2WSZepAAHXWcdLcAQhHwNDbxQomP_WPn4byLwPqrQ1nBaDifdkaVBjTbVsOH9UZbEhDi-CCdf-d3PuklpGFhMgnTGhTIfHmgegifePpXjfQWBjrE_-fDSg", "name": "The Nature Conservancy", "rating": "NA", "id": "90af6fb9fb926dde9f7103577cebc4150bbb1dec", "job_title": "Statoil-Gulf-Services-LLC", "place_id": "ChIJq-m4EX3AQIYRJkn4Lhccp2E", "address": "1800 Augusta Dr #240, Houston, TX 77057, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.42318089999999, 29.7345943], "type": "Point"}, "properties": {"photos": [{"width": 750, "height": 437, "html_attributions": ["<a href=\"https://maps.google.com/maps/contrib/106788706324997826205/photos\">Erika</a>"], "photo_reference": "CoQBdwAAAICw9vnc5Jiy3UQtURKCW9Wa2Tt5wngUXIMcvIFCQs2Kmj3DRlGSBQpTgxf6om5B-RUyx0jDC2IzwWtGS-fpyxGISEpD5L2CXSgtdhPKZo6nfsuGJHfEz1YJonT5N-unJnVYFSF19oEr08rQk-pSTcRW_wrboKM43yLvnFc-ANvbEhDiIZJIwr_l7SAJbbFOjNy6GhQHFG12qAHCBFpzQLP5jsnXOj-_cw"}], "types": ["point_of_interest", "establishment"], "reference": "CmRRAAAAEo2zdvSSm_Vqm18Xyi0S2OWKGOEeNnVidp0HMsPywOQUvKBuOuIRQ9HxbaDYH6htZ9vF-VrbAIo2qsNjGbIGrsaYS95Dw1FE6wTMvwpk1SFEWJIoXr0P5b8QOy6SQYavEhD-u3j1209FSLMC_OMXYegyGhQqjY3bXKqhsKklCt3wzrXMGP-1EA", "name": "Student Conservation Association", "rating": "NA", "id": "1c5ea7722fc0d99e9f7dfca55f5d9078224d51d3", "job_title": "Statoil-Gulf-Services-LLC", "place_id": "ChIJQcqBXfDAQIYRErawO-goGj4", "address": "2990 Richmond Ave Suite #400, Houston, TX 77098, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-96.038102, 30.055621], "type": "Point"}, "properties": {"photos": [{"width": 984, "height": 985, "html_attributions": ["<a href=\"https://maps.google.com/maps/contrib/110279808588468038448/photos\">Peckerwood Garden Conservation Foundation</a>"], "photo_reference": "CoQBdwAAABlJ3oO9Kp2Oyh4rW557no-AtNsODEPCa_nQQll-NIDkOIxGglKcrZyk4PW9cL0UHfqg4jdfBpTqyCYGaEmW-tej1uebd7Z43NRAsHZdMFGmJ8HES4rAyFdUKEQyLoiQMrqXEiRge5mnytpwVSNcew_9EleomCwb7U0TjFyLO7wwEhDiUQsWk9Gml0YOIq0xwN_YGhRafRg7pivBRfuUOU_3ZvjAyfqjDg"}], "types": ["park", "point_of_interest", "establishment"], "reference": "CmRRAAAA91WMOa3D-IpbMMQqGyrrkizsYW05KWNVZGNq6g6K41hLJUv--eL_az3IFErMnzjHWDg4tg5NAtyVBqmYlxjwpdieJaGSEDGevz9sijGY2NaQ2uBSvmAT_BX75K81EbaYEhADl8sGBocZZ4IR2Efs2VzfGhSDvzzmiCl65M_2tRC9iuB2JzCoIQ", "name": "Peckerwood Garden Conservation Foundation", "rating": "NA", "id": "e618a4c618cd67ce4f5fdc165f640220ab3b53b2", "job_title": "Statoil-Gulf-Services-LLC", "place_id": "ChIJmUR7pvHKRoYRIIl0o73bPGE", "address": "20559 Fm 359 Rd, Pine Island, TX 77445, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.64386449999999, 29.7515036], "type": "Point"}, "properties": {"photos": [], "types": ["point_of_interest", "establishment"], "reference": "CmRRAAAAFeRs6iIe4-O-zUbsLCBNsWH2MbMSth9vk2x00j01ewZl1QC7yQ84TuhJnfvqU6lTYFgE2kDu1-9JUn4Ffpt_oIUfqexkfTyUtdB5mU1UcTV9rE8JURNXs1CEUhATVF69EhDLs3NPhGNIIlJtGR_m_BtfGhRN4JcE7gcr7wi77-_aTeWxWi_w1Q", "name": "H2O Conservation Technology", "rating": "NA", "id": "30c07988ef8dfc62dac712b9d587daa4a36f2539", "job_title": "Statoil-Gulf-Services-LLC", "place_id": "ChIJIWZRKeHKQIYRXxta3wOMGGc", "address": "1725 Hwy 6, Houston, TX 77077, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.5705632, 29.7714443], "type": "Point"}, "properties": {"photos": [{"width": 3024, "height": 4032, "html_attributions": ["<a href=\"https://maps.google.com/maps/contrib/108143329814504597326/photos\">State from Jake farm</a>"], "photo_reference": "CoQBdwAAABy65qFWUdVdn5bHW-i5QZKDzRLu-5_EE4PFIm_LPttwJitWPKSyEGlAZbPvnFDk0WQMEDYlhlLaF0SiNssLqemQd_nyVUh-axbsUyNdC3XJiGe_8thRB2XeB_avBCkA2yd4GnUu3HVEtG-FiyPNMFgIj6JbythFtI9Lpq0bLNpHEhAdAVcKzgIB522_SQnM7C1sGhSEc8LK4H8XmNy6oqL8Fco5XD50Cw"}], "types": ["park", "point_of_interest", "establishment"], "reference": "CmRSAAAAW6UM40yOp_FBIuOawUHxCL2QhJ073F-rCWDphuGJcdZkdiA25_7zU2Yp7Tg84Df328NH2hWDuo1pYR72ZcHcT5NdiKBOk9-4sf9CzNY07ZeyfhdAqXWj75lL4UnvniBwEhCMTro9dQVVVRJ1f1lgEJxqGhT6Djlf21mBU6oHPj5-_jmQsj-hIA", "name": "Houston Audubon Society", "rating": 5, "id": "050a5458d86bdd1cee7b09678bd6256d0a20a73e", "job_title": "Statoil-Gulf-Services-LLC", "place_id": "ChIJlQOxwVDbQIYR2uX_TZl0TYc", "address": "440 Wilchester Blvd, Houston, TX 77079, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.56820189999999, 29.770778], "type": "Point"}, "properties": {"photos": [{"width": 1800, "height": 1200, "html_attributions": ["<a href=\"https://maps.google.com/maps/contrib/108765250995932379967/photos\">Audubon Docent Guild</a>"], "photo_reference": "CoQBdwAAABEKiBsUMsaJVCrSjZczn9Bv4bHprVBksExlYe6S3Cfg-NchVp_TDO-_c4tiQNewRVMTj1lN3T5MQL8DjeILNeBr1HxY521PCe0rZhrehj176PBmC_rJEo4IekV4w0BF1HyX6Dwtd3uWiAJGYeK2xJdvFHCy99TioPZk7TsnrnKAEhCO8DSlz18OfvclkJZiRVgPGhQWM7CvnTyYYqHM40ASGnNF9Xex8Q"}], "types": ["park", "point_of_interest", "establishment"], "reference": "CmRSAAAA5vgsZYCp5rve7dkrd0-LC3HyDIjoHrwYx47KiS4na80QtyQ9jb_p1Xd4o-M26JHTlX67WnQbcvuH8utZBW9vKAhGRMkjEdH-G0YY8oolELWdh3pfdq-B4Tcbc_rc5kEkEhAokZ9oe1ftF7hLDVqWFHdSGhSgFmYoU1hz_pubrzCzgQxQ0ETSzw", "name": "Audubon Docent Guild", "rating": 5, "id": "7ddd5daf76cc4979e2ba6b062322d1c77d5d1c07", "job_title": "Statoil-Gulf-Services-LLC", "place_id": "ChIJI9XyNFHbQIYRtwHb8EtTpeU", "address": "440 Wilchester Blvd, Houston, TX 77079, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.44932349999999, 29.7803218], "type": "Point"}, "properties": {"photos": [], "types": ["point_of_interest", "establishment"], "reference": "CmRSAAAAj04jgasyCDXV-D6cf6CBJWZFHjsGSDFipyimK5H5cqnVcyJxAGtjec7dUTVig2jYKcD0wrHv2Q81JYU6iYTVLsS_hInopx3ID0CAYCzs-YRIUe2RSmTPf52xfGbWnDGFEhBWMHt-iZMF6Td1iK-C8oR7GhS6YY95cY8Laqn14iaGuK9KuNvFvQ", "name": "Coastal Conservation Association-Tx", "rating": 3, "id": "7258b034e119f31e82320bca6e72781ee9f79d75", "job_title": "Paragon-Fabricators", "place_id": "ChIJcekacM_GQIYRPzL13cgQrPk", "address": "6919 Portwest Dr #100, Houston, TX 77024, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.47039, 29.655454], "type": "Point"}, "properties": {"photos": [{"width": 5312, "height": 2988, "html_attributions": ["<a href=\"https://maps.google.com/maps/contrib/101184977609161362375/photos\">aug4</a>"], "photo_reference": "CoQBdwAAAAuttAEEo2jBRdeMI3LLrX5gzp7gr8qqR6Vwfjv6pK1FXWPc3wEGwRYjQ249SeO49R1GcM0wYgJRQPHH3SIxNDmU1-R-nYi4rkn7Z4jk0L6DrSj0Y1RnkJK0xKH8AKaV3lXfMtZQPe1-AuJ8F5hwBKZ8va5Cruhg7qin9nlxOtCqEhAfts1h8IBJmKKZA2di3wYUGhSNN1SJKIJqh-t5BrKX8ger2Ye62Q"}], "types": ["park", "point_of_interest", "establishment"], "reference": "CmRRAAAAgBcdMFsc6lD10lHkv0Gr6780R6xpk91AIJt6GsSArw05PdQmtGicgJWNM2AmpQiDVA9RI2LpC-tMeK28TlusXIDYIrR2JE8eMYJTbus6dzOlRyNyQe-aK_qnatiCScJWEhDLQxY9SCH1TVixmZNxSmaHGhQqeH_L8Zl2SVmIqTgsqmi9yTer-Q", "name": "Willow Waterhole Greenspace", "rating": 4.3, "id": "0127506e8071350c2d48f0ca56e939045297a0f4", "job_title": "Paragon-Fabricators", "place_id": "ChIJR6_2zTzqQIYRsA7wExgfDWs", "address": "S Willow Dr, Houston, TX 77035, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.4003322, 29.7388505], "type": "Point"}, "properties": {"photos": [{"width": 1136, "height": 640, "html_attributions": ["<a href=\"https://maps.google.com/maps/contrib/117056878997299689379/photos\">Marisol Brown</a>"], "photo_reference": "CoQBdwAAAF3xOrPE6xdWGS8SfbUCaiuhuaM4yMOHYUBWkni3wUllkhczzjLFXTeJJoHsKSh6Olmnm-3AnokklhXKJQ76CKyr-sy1mIAZwWI-_2W23ZPA6tpeBgnZhv79EVggvjrR1BtDYlFGqiwIaX0gKil69-KMKFHGqVafBvP2wIKv4ZBJEhDwq0Ez7gFANuU5GbERl4OxGhT9HVYTM6VkGHHr4atYYMSzx5A6vQ"}], "types": ["point_of_interest", "establishment"], "reference": "CmRRAAAAE0T2_t9VXVMPoYymFsHpR46tHEhDT3SOQCHWIgNzkJo_CUVpXMdZGF4N99ZHfypBIrp-BJLwXx2cQrfq6oCSgUSf3yHggqbOcbcBFd3_lVbpdPa4Uv-YCLyo06tm3PnWEhC4wx4ZOaRGAFx6r95zcQacGhQF-peNCjyXXovqlcmtMkP1Fz6t2Q", "name": "Masters Fine Art Conservation", "rating": 5, "id": "a462c2eef4e22ea319485ae7b84f3d20756cbdd1", "job_title": "Paragon-Fabricators", "place_id": "ChIJp8u2bZvAQIYRbosnWz6cVmY", "address": "1612 W Alabama St, Houston, TX 77006, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.3876169, 29.794149], "type": "Point"}, "properties": {"photos": [], "types": ["art_gallery", "point_of_interest", "establishment"], "reference": "CmRRAAAA7vuXrp__3b7yJCa0WpFHO1vw3xGShX5HcKxP45KW7mOZrdVvufqwkw81tVHZPvPfDtehcxLzARqhbuNwgJKUis_udxRigv6ssRa9so526k6Ti4owhnfYc63La8mmplleEhC8aY2YbCS5sRt0qcNDEmyDGhS9IeWYd660RD1gDH36rHMVtiXCCA", "name": "Whitten & Proctor Fine Art Conservation", "rating": "NA", "id": "883a8c5ef35ab28e1630235ad65a6b16506a67fa", "job_title": "Paragon-Fabricators", "place_id": "ChIJ8YuXE6K4QIYRn1SF1hazFEw", "address": "1236 Studewood St, Houston, TX 77008, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.3858767, 29.7300997], "type": "Point"}, "properties": {"photos": [], "types": ["point_of_interest", "establishment"], "reference": "CmRSAAAA3RM-mnjpICtNJQ2u-IiEG_mdYLs1SqtFmyJ_1tIKs-io_eTg1v_yJ3wV3MXdPniNJkc4nRc-8MTKU2mIUZyHp8IfKnXzXgdw7TG5s9zCce29SMY-fcamFaq7goYSreNbEhC-ckHthKxzY6btaJvHxnm3GhQNoOLhS-o7b6lAjANIEw8pKHk-HA", "name": "St Mark Fine Arts Conservation", "rating": 5, "id": "ea2d4bac6d74716b33f456dff3aae0cc0b43cca3", "job_title": "Paragon-Fabricators", "place_id": "ChIJKbDEoXm_QIYRcRFBlp0dE8A", "address": "4901 Main St, Houston, TX 77002, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.483218, 29.7482286], "type": "Point"}, "properties": {"photos": [], "types": ["point_of_interest", "establishment"], "reference": "CmRRAAAAmdvO4cvFJSsHwDnuAMsH_-X24-lPfVGaUkWOClVfpxkfNECj9wsNINsG2nmg-SE2_QZ46Pcnldn929JKXUGQf2XLo8npb8tmNkgtsiq5a_01F7lLSWLkBF9nHuWlVDwdEhCl-rZITzwLPuTpH-96Ekx2GhT812w5os77kR0jAY6LAHUNWLyo-w", "name": "The Nature Conservancy", "rating": "NA", "id": "90af6fb9fb926dde9f7103577cebc4150bbb1dec", "job_title": "Paragon-Fabricators", "place_id": "ChIJq-m4EX3AQIYRJkn4Lhccp2E", "address": "1800 Augusta Dr #240, Houston, TX 77057, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.42318089999999, 29.7345943], "type": "Point"}, "properties": {"photos": [{"width": 750, "height": 437, "html_attributions": ["<a href=\"https://maps.google.com/maps/contrib/106788706324997826205/photos\">Erika</a>"], "photo_reference": "CoQBdwAAAFluwdJjL3D7ARQ1kWFYXm-W6_urzexmYaUGX89ybUNRBIXGHkBh0XF2r4-hVibQeY3mTldROmKbE_FwlVQFi_oLfRzQHnLw7Cte9aV-ZUL_Z3yqwGUkAY4Vd_9ByxwSp0kUyB1Qm0sdpxcpR4pAviG8_no_Aip0Vhs73dzTatLIEhAPDVmkMgEvFvt8W1lUADteGhRCQ_OM5b1wUDSjbf4aMDaa45YuyQ"}], "types": ["point_of_interest", "establishment"], "reference": "CmRRAAAA0guwXZPgdV93vzbL-FwOzQGAM6AujGNhXQsv--kEIlhOAMsHn6nFmsDhbcdFM180eZHgX7a5nd8RJ7UVT1wb6vnxkFC5htPsUPutXFBQpHj9lryLhV3OfK9jHRxdFKTyEhDfV60kPKNMZ9VJoDNfYg8sGhRMuBXgLxx8C6UsRKpm5g4T_3nWfg", "name": "Student Conservation Association", "rating": "NA", "id": "1c5ea7722fc0d99e9f7dfca55f5d9078224d51d3", "job_title": "Paragon-Fabricators", "place_id": "ChIJQcqBXfDAQIYRErawO-goGj4", "address": "2990 Richmond Ave Suite #400, Houston, TX 77098, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-96.038102, 30.055621], "type": "Point"}, "properties": {"photos": [{"width": 984, "height": 985, "html_attributions": ["<a href=\"https://maps.google.com/maps/contrib/110279808588468038448/photos\">Peckerwood Garden Conservation Foundation</a>"], "photo_reference": "CoQBdwAAAEpckTeZG4zoFOdfhUKj6x4pRJU108H2rIHdADQl99iBvbvOgp8-6Mg_7SAMHU2AbHhqRHgYcbW1Ws4FmPQCFDoX83j6pnI5XDaGnuuInNoUAbvfJM_L933TudY5zDY-cDBV1zToHE4pE0rvA8RYALtznVGWGhTEVeFNs2OUb-EuEhB-DHZx78A7RO-E7WVseNcFGhTuuUOEJnekaK7CTm4LiIy2_W71LQ"}], "types": ["park", "point_of_interest", "establishment"], "reference": "CmRRAAAAwGr0_ZT5PuuIecqYTGyMSrRGBf_MkJrnjmwCPXPwWORUSVznQ7VIcy5IdDNkNgXxPZm1CNMh9uk_4H4YGiYMJe9QTSxmMZj-45H3I2yG7ppadgAuPwAY63KHjm_tiTBdEhBSjOEjPIbgdY-wrbjCQDI5GhSm_fnI2k8urtCG6tc3PhzSnULa1A", "name": "Peckerwood Garden Conservation Foundation", "rating": "NA", "id": "e618a4c618cd67ce4f5fdc165f640220ab3b53b2", "job_title": "Paragon-Fabricators", "place_id": "ChIJmUR7pvHKRoYRIIl0o73bPGE", "address": "20559 Fm 359 Rd, Pine Island, TX 77445, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.64386449999999, 29.7515036], "type": "Point"}, "properties": {"photos": [], "types": ["point_of_interest", "establishment"], "reference": "CmRRAAAA4RqLWBoizra9UpPQkYuISx0DwmWhOeo8vsJyKR4jbaCl27uCBP7AbSgX0ZJd0zvcbhDxHb6twxug_rGdadSw-QEMpdK-Yazq9ObbJipCz-mi4_6a3lHTh9NuPZrqRL9WEhCpvT9L-N_Y8MKlsGxBnh8yGhRFvijhmohpgn50ud0nvjNTZWnEyA", "name": "H2O Conservation Technology", "rating": "NA", "id": "30c07988ef8dfc62dac712b9d587daa4a36f2539", "job_title": "Paragon-Fabricators", "place_id": "ChIJIWZRKeHKQIYRXxta3wOMGGc", "address": "1725 Hwy 6, Houston, TX 77077, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.5705632, 29.7714443], "type": "Point"}, "properties": {"photos": [{"width": 3024, "height": 4032, "html_attributions": ["<a href=\"https://maps.google.com/maps/contrib/108143329814504597326/photos\">State from Jake farm</a>"], "photo_reference": "CoQBdwAAAMt8R11Bw77L1eonFH_5L-4uRXfo78xF4kNQaGZF11iS1NuEpvjh266tMb5Muiev41UfJjSIzQjijHYuVmWXAw7S0mZpB0DBIOmsNI7FEuFhbABI42Xr1NodfTEbhLWA4rBWcs2499WCAXdGd-Em9DcZaHTrUk6Y2kwsDeKqcxjQEhDelSod3DgC_y46xNc9hrL1GhQxZTQU8RX27pLvwLEBc1N9UKTZLQ"}], "types": ["park", "point_of_interest", "establishment"], "reference": "CmRSAAAA2XHo_xbnrDmRA4nu4G_pjS_suuPX8mkolX3YEf60R-XzHMMV62w4HNmLiCqWKZoABMhLDZ96kZKl0W1QZfKXZjECbnoL7rT3WS6IKj5ppLJGeWdTTtrPBNQ8j12O-GoLEhCuC_dj0I8vx6R2k6oB-9ATGhR9y9TNQ2m17B1L6lV6Qes_NDlqvw", "name": "Houston Audubon Society", "rating": 5, "id": "050a5458d86bdd1cee7b09678bd6256d0a20a73e", "job_title": "Paragon-Fabricators", "place_id": "ChIJlQOxwVDbQIYR2uX_TZl0TYc", "address": "440 Wilchester Blvd, Houston, TX 77079, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.56820189999999, 29.770778], "type": "Point"}, "properties": {"photos": [{"width": 1800, "height": 1200, "html_attributions": ["<a href=\"https://maps.google.com/maps/contrib/108765250995932379967/photos\">Audubon Docent Guild</a>"], "photo_reference": "CoQBdwAAADJY3sN-sFTceX_ZRXj0myXro5-Q6p4RCexNy8ORoFkLNa9J-Wl3qIhwwZHpLJbLqCf7wW301hgWAFCyilFGD6U8J-Eb92b_JV2GmU-SF7W4jk36TW74y-MlAlLG-rU7x1ra0kcqk0q6PlUsOwregYV8sHaeDQR6sO2Jp_5E7uRWEhCRvwi20vVii6n8By_7bf_xGhTKMvnpfr4lIvEVzHI3gltHwMgYyg"}], "types": ["park", "point_of_interest", "establishment"], "reference": "CmRSAAAA9ND-MBfVeF-t_5oyKstnE4R_zYYFAA_h3FaXC1-336a5xxKGpNi4ygYE3E6oRH7dTf5OiGM2N8FtdVuV4kgnmGo3SSJESZyiWnjLU4WAjOTbLKR35xpZwV3bBPmv_raaEhAxQg67bCTqos7BV2JLYt8rGhQGlSm3ofomBugavY9mDshKZzhc3A", "name": "Audubon Docent Guild", "rating": 5, "id": "7ddd5daf76cc4979e2ba6b062322d1c77d5d1c07", "job_title": "Paragon-Fabricators", "place_id": "ChIJI9XyNFHbQIYRtwHb8EtTpeU", "address": "440 Wilchester Blvd, Houston, TX 77079, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.44932349999999, 29.7803218], "type": "Point"}, "properties": {"photos": [], "types": ["point_of_interest", "establishment"], "reference": "CmRSAAAA5d3DzQiOswRXugQ6SN5K0U-3PkxjfYQBOxBJsb-5G2xjpK_p575c9nk3JkEEYJGihUSLPo62ZeMdoGnEWFwhFkjZUDB4RlO10M1EFozkDn5yAU4vfbaijcRq4VE7cMxNEhBrpLQqbQaPz0GuVbenzCR9GhSeDiAskwDnT8ll5TiGNJFYQ560kg", "name": "Coastal Conservation Association-Tx", "rating": 3, "id": "7258b034e119f31e82320bca6e72781ee9f79d75", "job_title": "Lonestar-College-System-1", "place_id": "ChIJcekacM_GQIYRPzL13cgQrPk", "address": "6919 Portwest Dr #100, Houston, TX 77024, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.47039, 29.655454], "type": "Point"}, "properties": {"photos": [{"width": 5312, "height": 2988, "html_attributions": ["<a href=\"https://maps.google.com/maps/contrib/101184977609161362375/photos\">aug4</a>"], "photo_reference": "CoQBdwAAAPousA6PsWpu2NI72JhoJKtsizn4p1uMIUNX6IzLX7rttdJ20LcoV20WzzZy2eRuneitp8zxg_drAcU2oerxizCaVvh7MhMBUk6fpBUdzZXcNEbm9IiUzX6K7S-LXyrmanAKSEEAxnhW9ssTg0rsPJCjKT4E4nbfNwrJxfdtB9HBEhCI-_W41Bu0qMek3dNikuLbGhRtCjaDqqkoFJqCL3YBoPX727PMpQ"}], "types": ["park", "point_of_interest", "establishment"], "reference": "CmRRAAAAszGmrVJitTWAz8TPEMdpGIWEfi5xM-Bf_jWfnZcTn6lb6XDhmehPX-LvVbaU2Z6I06y-zhPF1swOJWo0SzfjCWdZp72izAslqQGOWk66uUD3Z20lYNABrxO3mS0EmC5wEhBVpJwCLz6E_7TqWI5fOk5uGhS1XbUKW0rKEfSQLuPXTu7kD6-G4Q", "name": "Willow Waterhole Greenspace", "rating": 4.3, "id": "0127506e8071350c2d48f0ca56e939045297a0f4", "job_title": "Lonestar-College-System-1", "place_id": "ChIJR6_2zTzqQIYRsA7wExgfDWs", "address": "S Willow Dr, Houston, TX 77035, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.4003322, 29.7388505], "type": "Point"}, "properties": {"photos": [{"width": 1136, "height": 640, "html_attributions": ["<a href=\"https://maps.google.com/maps/contrib/117056878997299689379/photos\">Marisol Brown</a>"], "photo_reference": "CoQBdwAAAIZQY6YWDoFhy2M69B17Ux5xEAyqjfv2CVbiHcpIw9l8kxP8tAuRlqv02JRfVUMAbELFCFYxb88kM1BCRwoPoJVnzFhOG3vdEZyxmkijLZK3ikc8AZGq_nJWyBjCQqnhEdMRQ5PXlQiHLuwHtVla-XsE8ROg_zfRSMVVUbXaXRXSEhC0OwYATuIldc6EKVC4mO01GhQTR5R6Zfd9x-b9e19jbaFArFaJHw"}], "types": ["point_of_interest", "establishment"], "reference": "CmRRAAAAiSgzsqKB-TmvTYgwW8PVIXoZr8C4OTu7yz634ORpXtozLRacrc5Xp8rzbq_mXUcmRy5lxTrLPxgyK1INC8HZ35WYYG1Xh-NZv7xuRp08f8jIJgBaVic1bmJYl8Cupcy2EhDHu7yGXlun5U7FmBTRAqrIGhSMBqCIu8fglY_kD7QTSkbHkrDYEw", "name": "Masters Fine Art Conservation", "rating": 5, "id": "a462c2eef4e22ea319485ae7b84f3d20756cbdd1", "job_title": "Lonestar-College-System-1", "place_id": "ChIJp8u2bZvAQIYRbosnWz6cVmY", "address": "1612 W Alabama St, Houston, TX 77006, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.3876169, 29.794149], "type": "Point"}, "properties": {"photos": [], "types": ["art_gallery", "point_of_interest", "establishment"], "reference": "CmRRAAAAlePzg4iBDZXyV_6tjhjB4nJo1sEl9V5oAVsAgScnYWNjGer7Fb7nBO0xJU6i3f3tCr7yZ03H0OL5hLWx3LUYLir4FoopLL9929cqHJse1yOourvzQEZO1kSe4ZPR16BdEhAGBoiP__UGFssJ6M-WDC44GhQIC_uGjg26IiW5ja-S9JorWZiTWg", "name": "Whitten & Proctor Fine Art Conservation", "rating": "NA", "id": "883a8c5ef35ab28e1630235ad65a6b16506a67fa", "job_title": "Lonestar-College-System-1", "place_id": "ChIJ8YuXE6K4QIYRn1SF1hazFEw", "address": "1236 Studewood St, Houston, TX 77008, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.3858767, 29.7300997], "type": "Point"}, "properties": {"photos": [], "types": ["point_of_interest", "establishment"], "reference": "CmRSAAAAzJi9pJmC7KocYNUvQDnxn96gw5GmuLFwTBkzUog-kWVVAvKZ1Jr2CvZH-wfC8-3rz1bCJ3qKqmReyX3Mnf26ZjMQ5e7hUCH2I6tZV-nr5y9QM56oTQb3gatfB0nL0YrVEhC7hE2cnUBKvD3tE7KkidYNGhS1PM3-Q14Jq6lH2KacZLYeaqHfGg", "name": "St Mark Fine Arts Conservation", "rating": 5, "id": "ea2d4bac6d74716b33f456dff3aae0cc0b43cca3", "job_title": "Lonestar-College-System-1", "place_id": "ChIJKbDEoXm_QIYRcRFBlp0dE8A", "address": "4901 Main St, Houston, TX 77002, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.483218, 29.7482286], "type": "Point"}, "properties": {"photos": [], "types": ["point_of_interest", "establishment"], "reference": "CmRRAAAAKw9W-Iss32NSdCgGiWo29_3KHf5vb_VdMOPDUYdQPTrDasIfFO2ONMxHzAmkWC5MFKGEco1qPvmdzztvUSK7a_GUGHwYJVuF4dqKbFxwNTZbmNrPBs74mcBNCKHG8byCEhBVsDpY8UuCZYse3pXPTqj4GhRx_P7mAnA8749ZGVoHkAWZQ5DZQw", "name": "The Nature Conservancy", "rating": "NA", "id": "90af6fb9fb926dde9f7103577cebc4150bbb1dec", "job_title": "Lonestar-College-System-1", "place_id": "ChIJq-m4EX3AQIYRJkn4Lhccp2E", "address": "1800 Augusta Dr #240, Houston, TX 77057, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.42318089999999, 29.7345943], "type": "Point"}, "properties": {"photos": [{"width": 750, "height": 437, "html_attributions": ["<a href=\"https://maps.google.com/maps/contrib/106788706324997826205/photos\">Erika</a>"], "photo_reference": "CoQBdwAAAP1UvtRzF3ggJ66UMY_K30LgUqWBLsd70ilkTRc5FbyeYE9-SHkc6pjTJ1UWQiIPFTqcGr3MVJZS_ZTcnBTW3zZYjvFVj-ovelD1dURrEOSpS2cC9pkvlUfYbivV_b75JnFYI97uNl-QVC-dN02dYCaFFTm42CPj2tc6KGq9VT--EhAmwKuQrbIdxf8jx4b38xY1GhSqGHZx7nUR4XS4_DI8PRJvXEH6lA"}], "types": ["point_of_interest", "establishment"], "reference": "CmRRAAAAUkpy0E-tCxOP6J5MKrnqfc7ip5hWb4UguaMzjLHsjPsytmrreIke8evV78fL9hFy3TjXI_VxIk9AUQ7g8UDVanvfzffJ_jNqiojQVnKKS157ngg2bp9T2l0ctjDfigeyEhDHaJmd7u2XIbgDcjil3GX2GhS5GPerbmnsDSudG5qVyXQDXZDLQA", "name": "Student Conservation Association", "rating": "NA", "id": "1c5ea7722fc0d99e9f7dfca55f5d9078224d51d3", "job_title": "Lonestar-College-System-1", "place_id": "ChIJQcqBXfDAQIYRErawO-goGj4", "address": "2990 Richmond Ave Suite #400, Houston, TX 77098, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-96.038102, 30.055621], "type": "Point"}, "properties": {"photos": [{"width": 984, "height": 985, "html_attributions": ["<a href=\"https://maps.google.com/maps/contrib/110279808588468038448/photos\">Peckerwood Garden Conservation Foundation</a>"], "photo_reference": "CoQBdwAAAC-b95z4wvj3p5NhZqfMc6-sHxOh__uywpm2PwjPe5AazGiyE0WoozHiItMckxiTzp4dgNUbfAS3KaoxkvqLhLzXLFzrOrcydviwOo9099ZTY1AQwfT75__vetPKTSQ8OKRD4HtPsUMeCwEt1Yzv3br3Y4D7XE0uyz2KECgKx9urEhCQ0HXzRviINTtkelO2wVWyGhRXWmOpNNeh9-X0f2WoRLd0HBL6FQ"}], "types": ["park", "point_of_interest", "establishment"], "reference": "CmRRAAAAKUfigJF3231LKc4ldGvQoQPZAMAkvltstO0DIPyvRjvWjh5s1UvJQG4U2rFb_BV5zL29ZIav7CYkp9aHbArMqHiUxgUslR8d7ZVSE_Z16ND0pOu0sVo9irRiygqAzrnIEhDIlVxaMhnKx_P6vI7KNst1GhRlpppBPccDeAUfuvJmZV6t8Ynm_w", "name": "Peckerwood Garden Conservation Foundation", "rating": "NA", "id": "e618a4c618cd67ce4f5fdc165f640220ab3b53b2", "job_title": "Lonestar-College-System-1", "place_id": "ChIJmUR7pvHKRoYRIIl0o73bPGE", "address": "20559 Fm 359 Rd, Pine Island, TX 77445, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.64386449999999, 29.7515036], "type": "Point"}, "properties": {"photos": [], "types": ["point_of_interest", "establishment"], "reference": "CmRRAAAAlipxFrBnt2XO60vGjA9fVYm61TFMrjxub2D-MlxrR0vPax6jg-OdJB6PfW02AOBdhfD9v86aDeO9lJSwTRyjWGxAxxzeQKeg6P-nmGD3a0gWZe96Y9aRjRo_MvJHm8jiEhB6OPUNSt9DCho0g7T1F2EDGhS8_S31kOw_7iQtSf7PD-bzvuEMZw", "name": "H2O Conservation Technology", "rating": "NA", "id": "30c07988ef8dfc62dac712b9d587daa4a36f2539", "job_title": "Lonestar-College-System-1", "place_id": "ChIJIWZRKeHKQIYRXxta3wOMGGc", "address": "1725 Hwy 6, Houston, TX 77077, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.5705632, 29.7714443], "type": "Point"}, "properties": {"photos": [{"width": 3024, "height": 4032, "html_attributions": ["<a href=\"https://maps.google.com/maps/contrib/108143329814504597326/photos\">State from Jake farm</a>"], "photo_reference": "CoQBdwAAAGuOL_pNsJrJ9wYPIKLTk3xkvTwajYM1ROo7BjRd8xx3X6SZx3crHEtlKgk53_RhoycMo_dkmDg3d9v17tcxbQfmsVPR_oX3b6I6ZkMfhSx27t2qkFC0Er33nHsIrIZ-3BLSgFZa1u57gIGbn7hTlZjXmGed7XeX8vGYUHBb4Mm8EhD6wEK2ifHd57jmmX-qsxPbGhTbw2CqHdJkwycUHnE71tW966xnxQ"}], "types": ["park", "point_of_interest", "establishment"], "reference": "CmRSAAAAPNhdOOTaX6dXS336wj7VFo1xyQcwmGNU5zTC_VqMQHfSTi5g0bmytkQ-0gvUq51ngfB9M-qlBjgZGUsfveGnGgcKz7UlzyrKUYjOMtACLxWHu0c77ppYbVZFKlPncWF2EhDFgfdtoE4Dndp1v4LQfCX5GhRPSy1szFB34Aydhdv-a6oTW8aSvg", "name": "Houston Audubon Society", "rating": 5, "id": "050a5458d86bdd1cee7b09678bd6256d0a20a73e", "job_title": "Lonestar-College-System-1", "place_id": "ChIJlQOxwVDbQIYR2uX_TZl0TYc", "address": "440 Wilchester Blvd, Houston, TX 77079, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.56820189999999, 29.770778], "type": "Point"}, "properties": {"photos": [{"width": 1800, "height": 1200, "html_attributions": ["<a href=\"https://maps.google.com/maps/contrib/108765250995932379967/photos\">Audubon Docent Guild</a>"], "photo_reference": "CoQBdwAAALXeYquisTY3yGXT_K5Mr0STTWnCXsPA03j8U89ohoVf_XQXzM9ZZ5-etfQPIl8MdcyLtCPw2hD-pe2jsR-upOY1kUSi95fGyCFMJ23dQQKXZFcCoeYVLCoLvhIL436ZeqGsIe4NUvwvVNGkRjyDXBxuKMYnEa4LJO2R5CDkPPAuEhDd7mPNIPqb57_d8tlwrJh1GhSoA_5vpNgEhADLW627k3ReEtdg4A"}], "types": ["park", "point_of_interest", "establishment"], "reference": "CmRSAAAAaGr1Xw97fUl529E57Uu_n8ole6a9RzmFdkUFUZ-AhgCWhh9xUoAVMhvtAcRWx7Pg1Q3RTQQkTWNAYZcyd3uiJmQ76mlCdJYmnuhV9XddEW6kej8wCVAdbMTJdy5CZKrxEhC2VyGhG4DFhcjI501pnuJcGhTRh0-GQCoco12aFFHrW99jDy2bcw", "name": "Audubon Docent Guild", "rating": 5, "id": "7ddd5daf76cc4979e2ba6b062322d1c77d5d1c07", "job_title": "Lonestar-College-System-1", "place_id": "ChIJI9XyNFHbQIYRtwHb8EtTpeU", "address": "440 Wilchester Blvd, Houston, TX 77079, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.44932349999999, 29.7803218], "type": "Point"}, "properties": {"photos": [], "types": ["point_of_interest", "establishment"], "reference": "CmRSAAAANqSo9qUbzF9BXt4dg6RWL0WIZ5WiBj7lbucWxlJJnMzfVePBwmQ_aUulsQYF45kGkuvKsj3Nf7Uy7ytwcPrKNyhRR46WNcUt6Hv0ttBMDrhwBlVCZEsIJAWtmiwZr4YLEhAHGiyPqE5wVP3CMUIt0XpdGhS8Ypf9r6yU7G1Hs5A3z8e_v_krSg", "name": "Coastal Conservation Association-Tx", "rating": 3, "id": "7258b034e119f31e82320bca6e72781ee9f79d75", "job_title": "Nalco-Champion,-An-Ecolab-Company", "place_id": "ChIJcekacM_GQIYRPzL13cgQrPk", "address": "6919 Portwest Dr #100, Houston, TX 77024, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.47039, 29.655454], "type": "Point"}, "properties": {"photos": [{"width": 5312, "height": 2988, "html_attributions": ["<a href=\"https://maps.google.com/maps/contrib/101184977609161362375/photos\">aug4</a>"], "photo_reference": "CoQBdwAAAG41YZkCHUcWyfb2hwdmNH7yNwrRVZYJsgILmQEyAfpoh7Ba6LvU3CUu8gQBm_L_qbox1s2sP5DH-VGArF3wE11M99kAQOCxX5CHy5vrJzyyL9jE8ksibUBq1eNUi1EXqw7clA-tzMoTHYzQ6rX6o4vjSZbbZIqFOjBWDAEU21spEhAgceZs8FUPuNzQdfoMC-hsGhSI14y1MnJaSOXPnMpd5hvZLWuy1g"}], "types": ["park", "point_of_interest", "establishment"], "reference": "CmRRAAAAlhagja4xNsjn0yxMvJKm1KF3804pdhMFMo7lNNeS8od7e-ogBPfcmOU-1YACRFPd-CPdDkTQKEgoh-U8yrLAzyUp-yWmsIic2njhnvMmEby5fzHOaIiejk1e3ebRbM30EhCUUvcsXBvWuNPcRd4HjcorGhRSftbYwuJUnyqUocGn8RgKY3OOWQ", "name": "Willow Waterhole Greenspace", "rating": 4.3, "id": "0127506e8071350c2d48f0ca56e939045297a0f4", "job_title": "Nalco-Champion,-An-Ecolab-Company", "place_id": "ChIJR6_2zTzqQIYRsA7wExgfDWs", "address": "S Willow Dr, Houston, TX 77035, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.4003322, 29.7388505], "type": "Point"}, "properties": {"photos": [{"width": 1136, "height": 640, "html_attributions": ["<a href=\"https://maps.google.com/maps/contrib/117056878997299689379/photos\">Marisol Brown</a>"], "photo_reference": "CoQBdwAAACzlpHtrTYuJRnz0EMHcmruBZC9vmtCRM0GNFBeambTZNoaB1puSYBMOx_njTo2oJQlHNzkZHJC9XcQEWree9gquGkSUaSrqEq5S7L6e5VIcYSz6LprmsLiYz9S3PKYcMaMkmlq7pZSF8gJdoM_qF-TevmB-CKTrcLjZS-kS3QeMEhBSuz13J_5L-glfn2h10gDWGhTZzk4PH_FjsY1bNKaDxJEBSH0ykQ"}], "types": ["point_of_interest", "establishment"], "reference": "CmRRAAAAROFKPAn6Rf-yof58GEYbk2hNej00Sfxg5mKnN9zZg7p3OL1Pwo939iSK73kVxSr8zRmNTTjh8407wjg275FFwz0py2FV_X3yLjeT9IvbgWpna62EYme-a3P6nm3vmxEvEhDFbJZimWF388XUgkhysgigGhTbwiG4a33Z-tW70T_C4xsr4yQA5A", "name": "Masters Fine Art Conservation", "rating": 5, "id": "a462c2eef4e22ea319485ae7b84f3d20756cbdd1", "job_title": "Nalco-Champion,-An-Ecolab-Company", "place_id": "ChIJp8u2bZvAQIYRbosnWz6cVmY", "address": "1612 W Alabama St, Houston, TX 77006, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.3876169, 29.794149], "type": "Point"}, "properties": {"photos": [], "types": ["art_gallery", "point_of_interest", "establishment"], "reference": "CmRRAAAA4txtKxNbERvY_KbUAisVdbA4FOuaT_PKt9ayCVDekfpu1fzFKzjV9nXmmlvuyCtoOCJLXkfxDA2BrEsyzAaVAPSRC-ToBdXReTfJpwYu8Rips7nyRWlVnnBywb1cCO-_EhC5YraxRvxsI4v_HmY0hgELGhRPhR38-KGHo4qNBgMcEuDyCdXDqQ", "name": "Whitten & Proctor Fine Art Conservation", "rating": "NA", "id": "883a8c5ef35ab28e1630235ad65a6b16506a67fa", "job_title": "Nalco-Champion,-An-Ecolab-Company", "place_id": "ChIJ8YuXE6K4QIYRn1SF1hazFEw", "address": "1236 Studewood St, Houston, TX 77008, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.3858767, 29.7300997], "type": "Point"}, "properties": {"photos": [], "types": ["point_of_interest", "establishment"], "reference": "CmRSAAAAKXgKnzhL-HcbNh-YXNK292fzPG1STATGe_KCfVJi8oytooV0Jq_klzXmy7PgQ-ld_FUVP36qs3P3xZlFsVH1RE1aPEh526AFJWsVIPneUdDeX4EkNWOOYQW-IHP9CNMuEhDBat9Oa5k7yjB2jnkdHVeGGhQ2ME4LT8sJYhrgwiXK6h3Sbv3Eyg", "name": "St Mark Fine Arts Conservation", "rating": 5, "id": "ea2d4bac6d74716b33f456dff3aae0cc0b43cca3", "job_title": "Nalco-Champion,-An-Ecolab-Company", "place_id": "ChIJKbDEoXm_QIYRcRFBlp0dE8A", "address": "4901 Main St, Houston, TX 77002, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.483218, 29.7482286], "type": "Point"}, "properties": {"photos": [], "types": ["point_of_interest", "establishment"], "reference": "CmRRAAAA3YXb3l2Z1mExi4dsuHLS88jH0FOHTjASVQ8iJ2OSt4-dPbqQYlCtbfw5MPCZrzwdlBA_8HfGXCPcY8xlkgVEpNUPJGFrk_ownouxdyDbb7_G7rvsdi7TcmA2dMEQQQqJEhBdhER5rvkU3rV0N9Iqh_Q6GhSbyKYzW3h-W7nyt3gCqgG5twjGpg", "name": "The Nature Conservancy", "rating": "NA", "id": "90af6fb9fb926dde9f7103577cebc4150bbb1dec", "job_title": "Nalco-Champion,-An-Ecolab-Company", "place_id": "ChIJq-m4EX3AQIYRJkn4Lhccp2E", "address": "1800 Augusta Dr #240, Houston, TX 77057, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.42318089999999, 29.7345943], "type": "Point"}, "properties": {"photos": [{"width": 750, "height": 437, "html_attributions": ["<a href=\"https://maps.google.com/maps/contrib/106788706324997826205/photos\">Erika</a>"], "photo_reference": "CoQBdwAAAPbv1Y7u5-MBcILEl9iO6C02okAn3WsVSYLUibl3Cg7eIEiONBihFfBFlK3jq7HPtiIwk23Hvvd9yFcTgKw9PVflM6tUvIS2WwlyCKlR1cdX5pTWMqAbKGrc9tRZGAiwzvSx6MZ8q_8kK9RJabpSvObOtYNDLYndrIFTpfbCk44PEhCQFU0VINg4qB-BznEGQzVjGhTlwwOQm5J7VGQjk_h74r3pSjc_8A"}], "types": ["point_of_interest", "establishment"], "reference": "CmRRAAAAXL3JMEoUQTvmn0fM23PfVsJ5q_FW72kCfCnARB0eOmVMP0czdrXpAzyLjU9rGettHjm16qLjHHbvHBwqC2A5EwmQLedlQ2aWfA0Iw2ekxXpbTjN8GjII_skc5NxSC59kEhAmrIFA0POGAzrxNDjs0Wq8GhSCleRHrlcM5rq8BPL7xbsSxCJy2g", "name": "Student Conservation Association", "rating": "NA", "id": "1c5ea7722fc0d99e9f7dfca55f5d9078224d51d3", "job_title": "Nalco-Champion,-An-Ecolab-Company", "place_id": "ChIJQcqBXfDAQIYRErawO-goGj4", "address": "2990 Richmond Ave Suite #400, Houston, TX 77098, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-96.038102, 30.055621], "type": "Point"}, "properties": {"photos": [{"width": 984, "height": 985, "html_attributions": ["<a href=\"https://maps.google.com/maps/contrib/110279808588468038448/photos\">Peckerwood Garden Conservation Foundation</a>"], "photo_reference": "CoQBdwAAANR3HLLGcHyW7sn2kjyNyiXMQAu4XNnEjfMCEFFiSfB2IIt09iMOOerpTiZbO7AbjQZQoclbSoBOZB31eylNY5J1KBgsr4kbVEEFlSrxXCDKplboyPa1GsB0uW_EuOsQLjM6lNCrX9gtRkzWZKBpY_G8WqCJEbubPGTA1whOv3KsEhB-xd3MvW93SVnOBQ21y0-CGhRhFZ_8RH6Yekj_5POxxOd6be949Q"}], "types": ["park", "point_of_interest", "establishment"], "reference": "CmRRAAAAcp4eK_89cwpjvnltjMgOjj-GbMb2vn8MMYdWwykEJyGR8GtCwqEUfu8VLCHZcbw3mfNDn1nn9BMuyJvk498_BqhIlIvTMdqaMceb09blj3E56BdzNvmuz53qkWVbVvwJEhCXZWaV-DJsZmgMzbImuMKMGhRaww9ndgpKTkPV1M-sZNINaC6WJA", "name": "Peckerwood Garden Conservation Foundation", "rating": "NA", "id": "e618a4c618cd67ce4f5fdc165f640220ab3b53b2", "job_title": "Nalco-Champion,-An-Ecolab-Company", "place_id": "ChIJmUR7pvHKRoYRIIl0o73bPGE", "address": "20559 Fm 359 Rd, Pine Island, TX 77445, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.64386449999999, 29.7515036], "type": "Point"}, "properties": {"photos": [], "types": ["point_of_interest", "establishment"], "reference": "CmRRAAAA_Q6jQ0SLHcHCkJC16NJ3hBXVGO2g4WlFTV89JQUQYb9MFVt1EKv2_Eysbs8L6qiK5pw4GUIiwlO7jd7htIxjOw-w5X4nhIiKRiphlPoWHNURs5CgRUsCdd5pApBNeEOYEhADuZ7vGF9Srd2DHndRhKuhGhQ8XC-iDcq-RKJO3Wy0c9eXKv0Kvw", "name": "H2O Conservation Technology", "rating": "NA", "id": "30c07988ef8dfc62dac712b9d587daa4a36f2539", "job_title": "Nalco-Champion,-An-Ecolab-Company", "place_id": "ChIJIWZRKeHKQIYRXxta3wOMGGc", "address": "1725 Hwy 6, Houston, TX 77077, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.5705632, 29.7714443], "type": "Point"}, "properties": {"photos": [{"width": 3024, "height": 4032, "html_attributions": ["<a href=\"https://maps.google.com/maps/contrib/108143329814504597326/photos\">State from Jake farm</a>"], "photo_reference": "CoQBdwAAAOllU9muUT9zf9F67ih-PGyxgr2WMIW0l-I7wxDsQcIydc6oL1lvtp3kJYCGjjcYoB2V4SqGgOdYLMoYF1TmYkidupMaqN5qTzuKxH0HJMWc0DIjmNyRbFFzS4YXDM-YZLoThte-1QSB9qrGxcOIQrJbTRms8hbWvo0Fs2Sd2C3NEhDjH8vvqgE9uwVRVpKrWBF0GhQe3NAciedow5rLbkGVttuzg01hIQ"}], "types": ["park", "point_of_interest", "establishment"], "reference": "CmRSAAAAXHY66otXgI6Tsx3MtK5NFEEvDkraY3lIRFL6fk0uvVoX1dOZwn0bDvUIjmtifH-7_2x1wp-n2SvPG1qq3Kd4lXChWnRAqISq-z3If0LItj7JZUciiL784eOb0gBe2JDlEhCqm0bKaqe2swEk0yMyT5khGhQ80-WZk7UXdzb1sTysslUvr4g00w", "name": "Houston Audubon Society", "rating": 5, "id": "050a5458d86bdd1cee7b09678bd6256d0a20a73e", "job_title": "Nalco-Champion,-An-Ecolab-Company", "place_id": "ChIJlQOxwVDbQIYR2uX_TZl0TYc", "address": "440 Wilchester Blvd, Houston, TX 77079, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.56820189999999, 29.770778], "type": "Point"}, "properties": {"photos": [{"width": 1800, "height": 1200, "html_attributions": ["<a href=\"https://maps.google.com/maps/contrib/108765250995932379967/photos\">Audubon Docent Guild</a>"], "photo_reference": "CoQBdwAAAM2JpLX-jwUI-KT8G6RuVzRUC1EtL1ZnSy_toDmjmswgdFOmZWRQihFPlE11f57C7TGIuxTZ51kb7g7mFuLRIRiqbSEKHKLOno72V3s34ts6EYgPleJMjbxfwx2W7BG_iiJmP3FXB55CSHZy_7TvPAfL68TcYUvACRd2eCOOQvs5EhCBjkSkQ0JjUxCe6LKFOjIbGhQ8_mS2Lv16LjG7l-gbcw2pUb2MjQ"}], "types": ["park", "point_of_interest", "establishment"], "reference": "CmRSAAAAAxpNQO0fdC0qqgR4b3El2ONSUQsqcMeKTLuHNX9zJXhoF_y8hS58-4_rvqxfjIdbTZQD6ytdLggNiwq_7zu-oIgk14srPYV4uk_LGSc_632ABhMlJxveJFKe59L_Y5Q5EhAEFihVKfnPN7D0ccWln0VFGhSBBOBvcxv8VShuVe-nmFXxSWtCsw", "name": "Audubon Docent Guild", "rating": 5, "id": "7ddd5daf76cc4979e2ba6b062322d1c77d5d1c07", "job_title": "Nalco-Champion,-An-Ecolab-Company", "place_id": "ChIJI9XyNFHbQIYRtwHb8EtTpeU", "address": "440 Wilchester Blvd, Houston, TX 77079, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.44932349999999, 29.7803218], "type": "Point"}, "properties": {"photos": [], "types": ["point_of_interest", "establishment"], "reference": "CmRSAAAA1OTX-1PakdQKYafdl7jnsG59Dtd5XjRbscbeTgxh1crbQc8MlrsFYaAQ0COo_EcG88tMGkvjy1TVN5c1A7CQEyeUkhh2neVKhwBEktVIHUwFznCrelBVsCwnLsrKbJxREhAbrB8AOXdWV5qY93swpRHDGhSj0QjstN4N89urDil_lu14O7E5KA", "name": "Coastal Conservation Association-Tx", "rating": 3, "id": "7258b034e119f31e82320bca6e72781ee9f79d75", "job_title": "Jones-and-Carter", "place_id": "ChIJcekacM_GQIYRPzL13cgQrPk", "address": "6919 Portwest Dr #100, Houston, TX 77024, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.47039, 29.655454], "type": "Point"}, "properties": {"photos": [{"width": 5312, "height": 2988, "html_attributions": ["<a href=\"https://maps.google.com/maps/contrib/101184977609161362375/photos\">aug4</a>"], "photo_reference": "CoQBdwAAAGO_xXr9Fb5unfGlujC9Q5L4JQIfRibBLnH7QazPYwE7VV9wLteiWSux1AJeE8CE28FPM4cMpc9ArQfmrufMKQGGNGonXO3oiPwntkgjfbetUvA4TL4BJde5mpXX-ti-Cbsd91ZiRs4G_GjD_Dc7LxFRoAVnb8vwgGRdr9d55Hk6EhABCXWeB95KF_3ASMpZqa_cGhQvJ4pIFl-3Cw7G2eto4mq4lp-qBg"}], "types": ["park", "point_of_interest", "establishment"], "reference": "CmRRAAAAy7wH8wk5NA9zA8ELm64wFJ5VxzYLtEcJLx0jSyBmg7eyhEmF62VoTU7XJPDgHlRRQS59_Nhc89dzEkYRwSY6bCp9CDT5HpKQfN_cHpoDf16cmOQkQGi3jiXE3InWDUVJEhAvMwpk8dLz31c87jn523OKGhS_vvKH-IDXaKRU3xtlDZtQFQGKOQ", "name": "Willow Waterhole Greenspace", "rating": 4.3, "id": "0127506e8071350c2d48f0ca56e939045297a0f4", "job_title": "Jones-and-Carter", "place_id": "ChIJR6_2zTzqQIYRsA7wExgfDWs", "address": "S Willow Dr, Houston, TX 77035, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.4003322, 29.7388505], "type": "Point"}, "properties": {"photos": [{"width": 1136, "height": 640, "html_attributions": ["<a href=\"https://maps.google.com/maps/contrib/117056878997299689379/photos\">Marisol Brown</a>"], "photo_reference": "CoQBdwAAAJnNMK5OL3qgB7p0JOtc5t_YS16-qb1cXQWYr_msQBvzauqxBOMNQjh5GFiekZ69ZyEQtDyiyv8Gxh3RaJdlBt2EGWJ3flATHKFa5w9-hj3RcpFUktNL8SDxz1mbUAKwl7g878Namjp-l8Ub16rffGNzMr5jA4RutmSWrxLw2p9rEhDzk3AuhfzYfYegEbW-IW2iGhSeGtsHV66oZ-tP4rl6On6zGs9xsQ"}], "types": ["point_of_interest", "establishment"], "reference": "CmRRAAAAbp7hQHzw8yIJ0K3rx3RKjrUVMC5-mlPgCAB0SFmoS8bhbc6T-BURPjMHXVjPe37ySvBHsbHV3wgMKR5IuXQg6lpw1tOiBsZkHmYB-4CPMPS2v_cTXj2v5V6pTesx4zP3EhA0dIxCN3_7Pl4etyMEq4UUGhSJX2z6hbGWoraU14p63s73RsTAKg", "name": "Masters Fine Art Conservation", "rating": 5, "id": "a462c2eef4e22ea319485ae7b84f3d20756cbdd1", "job_title": "Jones-and-Carter", "place_id": "ChIJp8u2bZvAQIYRbosnWz6cVmY", "address": "1612 W Alabama St, Houston, TX 77006, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.3876169, 29.794149], "type": "Point"}, "properties": {"photos": [], "types": ["art_gallery", "point_of_interest", "establishment"], "reference": "CmRRAAAAG7s8VSITpVHiPQfDXGSqfotiA8DISeeqtMQ-bSQskgzeSG6GoJ504_BPM7mGSvil9h3H2EWNwK0_kaCspEc7qsOaXY-z2LSoQDeZEZqEv_r33f23nSZE6IDYo5eOEQJGEhDY40dRZEd_4sqhSgiGj23WGhRLqruMjmBlgxjdT3YZxtuwRGNr_w", "name": "Whitten & Proctor Fine Art Conservation", "rating": "NA", "id": "883a8c5ef35ab28e1630235ad65a6b16506a67fa", "job_title": "Jones-and-Carter", "place_id": "ChIJ8YuXE6K4QIYRn1SF1hazFEw", "address": "1236 Studewood St, Houston, TX 77008, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.3858767, 29.7300997], "type": "Point"}, "properties": {"photos": [], "types": ["point_of_interest", "establishment"], "reference": "CmRSAAAAf_NDWnlS7WGs_vB8TMnD730Ei_TQIoGZ3EnOvhu6pG5eiin6tPRIvFBwKP0WQRCLS4CX86IqL_gmHKHcnSeNuEEfXCXFo8fVgrTpBUoQuaJ5jZOv9MMtRm-lhZDZrlU2EhCa2Ur7hvBfT2kEa0qeThPbGhRSuHl4lvU08Uc735xAoR9NqfM0xw", "name": "St Mark Fine Arts Conservation", "rating": 5, "id": "ea2d4bac6d74716b33f456dff3aae0cc0b43cca3", "job_title": "Jones-and-Carter", "place_id": "ChIJKbDEoXm_QIYRcRFBlp0dE8A", "address": "4901 Main St, Houston, TX 77002, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.483218, 29.7482286], "type": "Point"}, "properties": {"photos": [], "types": ["point_of_interest", "establishment"], "reference": "CmRRAAAA4gn3PDkOf8zSPy5-drMwvrk9YbhoyIgei_Q5TIGesmgTlSOh53RgZfsobclCWF8igFsE2uPDtYGbpjHBuD_tdUAFOrd7mzo4apv6QjNHOsj9ZWYvpDUFscA-Qk20X0G8EhAtt3T0JLwIeoYLf0gVZaw3GhR6502EZL84Tc1Eb66GRiNA6bgk-Q", "name": "The Nature Conservancy", "rating": "NA", "id": "90af6fb9fb926dde9f7103577cebc4150bbb1dec", "job_title": "Jones-and-Carter", "place_id": "ChIJq-m4EX3AQIYRJkn4Lhccp2E", "address": "1800 Augusta Dr #240, Houston, TX 77057, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.42318089999999, 29.7345943], "type": "Point"}, "properties": {"photos": [{"width": 750, "height": 437, "html_attributions": ["<a href=\"https://maps.google.com/maps/contrib/106788706324997826205/photos\">Erika</a>"], "photo_reference": "CoQBdwAAAFi8GpMbQHkaPB2-5MUnAxkfwGl15r9JJNavKyi0ocLtSN0dpVbMzLuQhN88L3HKB1fVgYfQBgDCeMs-9q1djqe9a1TeIVu7mDOsT9idye25f94vg2aiO7ISWV7VLEYzSjhze46knPE8DZha4WFIvcBl_OZraM1yw6vU0rL-En5AEhDzINMuDckY0NWpYheDOq7qGhQT2HqsxFOMGQmCDI-2-r0EbZoXhQ"}], "types": ["point_of_interest", "establishment"], "reference": "CmRRAAAAz-L5hOLQxi1zuksZhKkDHscpWA8gl5F6xu_XRl7BHH1LSgRF4CtVanMZWa-E9IAAckg5Yy-wdtiR_LEX39l2LkAmABYLOGIpdEWKIYzLHYOMjsJr32HGck0WRt40MTLxEhD2_rFaGMCwjfO5jBJ7XbDMGhSY9DNrNW9tGWdyuxJ1bYKsQ4IWVQ", "name": "Student Conservation Association", "rating": "NA", "id": "1c5ea7722fc0d99e9f7dfca55f5d9078224d51d3", "job_title": "Jones-and-Carter", "place_id": "ChIJQcqBXfDAQIYRErawO-goGj4", "address": "2990 Richmond Ave Suite #400, Houston, TX 77098, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-96.038102, 30.055621], "type": "Point"}, "properties": {"photos": [{"width": 984, "height": 985, "html_attributions": ["<a href=\"https://maps.google.com/maps/contrib/110279808588468038448/photos\">Peckerwood Garden Conservation Foundation</a>"], "photo_reference": "CoQBdwAAAIXvkziqQY3meRveGN0NJWNurfXLZ43wJdutmglh9cMdac7CUOsXtL4ClaAMNlBjjvZIg4ATxqIOHOndSm6GeNmFNKrx3yr1nwtNbcl0UbTmhECH4Oo6ameEBo1Rl5NbKELbeTsWgem41LlhOkXBuQvmtsehZX36VsdRSIbX8ir5EhCTDg7YjNKpW5EOI2ksZpiaGhSjfOZ8xj3ex63ARHgHcOu7Cn94Kg"}], "types": ["park", "point_of_interest", "establishment"], "reference": "CmRRAAAA5K5egH8ro_uoqQNiwZ6HrngfG_kLcP7ni8uZxxb4m7TWKKgoLY103ifPcjJhmxoIvRRGp57IDjIxnW0sdrV-g3Dngh5qxk9hrTNaC2SyEUEUW8Dou0_4flqm5upJva-1EhD1ASCvt8uWRngrux9wUDw3GhQuN6nlDkrcd3QqWM3ObQ2No2jzSw", "name": "Peckerwood Garden Conservation Foundation", "rating": "NA", "id": "e618a4c618cd67ce4f5fdc165f640220ab3b53b2", "job_title": "Jones-and-Carter", "place_id": "ChIJmUR7pvHKRoYRIIl0o73bPGE", "address": "20559 Fm 359 Rd, Pine Island, TX 77445, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.64386449999999, 29.7515036], "type": "Point"}, "properties": {"photos": [], "types": ["point_of_interest", "establishment"], "reference": "CmRRAAAANw-U64hRRlUu7KC0NcFtSdgTRt1muZmxT-_tn8_zZTRPYunPxyWZUq2-cWVaUDZ_SlHj-b01q0H7iLsmHjx8PPn_Ncsxxtm9n_aY3Z2ntq--ol940uX0JqD51dxEliZ8EhApLAANZwtXwvkqAq1UwqGzGhRijy1PvRBq-Ql190Rn-pG5pJ8zRQ", "name": "H2O Conservation Technology", "rating": "NA", "id": "30c07988ef8dfc62dac712b9d587daa4a36f2539", "job_title": "Jones-and-Carter", "place_id": "ChIJIWZRKeHKQIYRXxta3wOMGGc", "address": "1725 Hwy 6, Houston, TX 77077, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.5705632, 29.7714443], "type": "Point"}, "properties": {"photos": [{"width": 3024, "height": 4032, "html_attributions": ["<a href=\"https://maps.google.com/maps/contrib/108143329814504597326/photos\">State from Jake farm</a>"], "photo_reference": "CoQBdwAAABMKE3zmSrDYtdxrGmgWjMWEjP5SarbTvb8bWYQ0eUGE9Qe4lLjHtgUpPD0_MSKUR0YChP8tcgFZxVXiUypuLbrFC2AyXkNP3xK3OaKR204djLDIH8g1pISTRaPq3DeJH6lONCWgvrXDVi3okfrqUWkVSLi_kY2QQt2xxDY6nKD6EhCghXKOxInt_cQrfH_s1RyCGhQfk-roYPTqObolfhF9dQ6txCK_kw"}], "types": ["park", "point_of_interest", "establishment"], "reference": "CmRSAAAAPnMuaBLKi3fSNb8DeAoF-ShfuK9X6L9urpmL9fqh6qPvW636g4PlZaz3Fi5B8VRV65FpbNdYqoLl_hQY31JhLHh-nnuVVY9vM2VcowRa5rngZqcXcNpJkY1mVBeVkr5FEhD13yQddqiUUYoiZd2IQeHUGhS_WxJnkyWuUut9bKeb9NJfgGJUDQ", "name": "Houston Audubon Society", "rating": 5, "id": "050a5458d86bdd1cee7b09678bd6256d0a20a73e", "job_title": "Jones-and-Carter", "place_id": "ChIJlQOxwVDbQIYR2uX_TZl0TYc", "address": "440 Wilchester Blvd, Houston, TX 77079, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.56820189999999, 29.770778], "type": "Point"}, "properties": {"photos": [{"width": 1800, "height": 1200, "html_attributions": ["<a href=\"https://maps.google.com/maps/contrib/108765250995932379967/photos\">Audubon Docent Guild</a>"], "photo_reference": "CoQBdwAAAC085J0cf4keD9LXSPi82unYa-3-ej7y5vpLqe-meLjwiaRyBTi0gZF1nXahRoun-8_Cbb6Vn_I9HTrw0p9a6lncxYyrVug_PzWaInA-UWhFWcGnJAAwnIcqUTyhAGkYUmKArR9tjeUooum6Dsl0HbIxcJQnV5Q7-olZ3AvQqZfQEhDZwTCh0rOIBlJHBXR-G2MkGhTPXa4QtEl31cMfF335O-w7rbVAIg"}], "types": ["park", "point_of_interest", "establishment"], "reference": "CmRSAAAAFzyWJjEesNNgTUeROdDdyCwioXncQYBVYeVIvjJbX_gCZe8YfHdX3b0mlbGpyKvgyKmeg_ewRGRTpZebriSnHHdR75JR19NwKlVn3CTchQ0tlXTN_Y9LPl-8AiqKD5AWEhCMg1mJiYojIrBx1XbmMBukGhQvbdTiYlhV73elZtHn-02o81ICoQ", "name": "Audubon Docent Guild", "rating": 5, "id": "7ddd5daf76cc4979e2ba6b062322d1c77d5d1c07", "job_title": "Jones-and-Carter", "place_id": "ChIJI9XyNFHbQIYRtwHb8EtTpeU", "address": "440 Wilchester Blvd, Houston, TX 77079, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.44932349999999, 29.7803218], "type": "Point"}, "properties": {"photos": [], "types": ["point_of_interest", "establishment"], "reference": "CmRSAAAA7u7wQuBV4itugST2Qh6PAh8GkPVcNysrFhiuOdNKm5eX__Y9b96yrntUrWEndXOWo2wamFHYz35c78LgoO55b8U83O70WEfsJPRgRFUgfbLhLEYRhiiavX-MPi-QH1I5EhCZA1JHMDK-J7P3voyqofkeGhTIX9rkHmnmTm-8UYh8Ml33dtBV3A", "name": "Coastal Conservation Association-Tx", "rating": 3, "id": "7258b034e119f31e82320bca6e72781ee9f79d75", "job_title": "Franklin-Retail-Solutions", "place_id": "ChIJcekacM_GQIYRPzL13cgQrPk", "address": "6919 Portwest Dr #100, Houston, TX 77024, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.47039, 29.655454], "type": "Point"}, "properties": {"photos": [{"width": 5312, "height": 2988, "html_attributions": ["<a href=\"https://maps.google.com/maps/contrib/101184977609161362375/photos\">aug4</a>"], "photo_reference": "CoQBdwAAAHBfU32Z4tu9cHaRJAk6rpE_7rKUtFsFqnPvJn_wvFQZ_dUQA28dQYpoeIdEjB4K2Uhdp5WvMQ6OaI3Rk21RBWqW-Do3jhcKb8eyoskkqMDJGSOij6MJQeMesAfnlaRJsL592P96-w98gY5rjaithRe8QcEhAJCWhffvZKqlVEZhEhC0CFiKxbGDojj7pAYNMhTaGhTNocdxl7BMJg2Q3tItqxQiPLl2hQ"}], "types": ["park", "point_of_interest", "establishment"], "reference": "CmRRAAAAAdvqUVnsApiuxbO6J9TqZZO_5paQZvPSGDvnu-x9Q8YFQmD2eedB26RWFvYJjwn5ZBFuUdEr902WTaUlPrT0teuFIA736CpcfHgmNmTyoICUV9DvOfXes-4MGpnxdb2bEhAzYgQ32wMUPuXKnerWnnUeGhQOR86USXA9u1TbdJ3NMvZSJ4ojZQ", "name": "Willow Waterhole Greenspace", "rating": 4.3, "id": "0127506e8071350c2d48f0ca56e939045297a0f4", "job_title": "Franklin-Retail-Solutions", "place_id": "ChIJR6_2zTzqQIYRsA7wExgfDWs", "address": "S Willow Dr, Houston, TX 77035, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.4003322, 29.7388505], "type": "Point"}, "properties": {"photos": [{"width": 1136, "height": 640, "html_attributions": ["<a href=\"https://maps.google.com/maps/contrib/117056878997299689379/photos\">Marisol Brown</a>"], "photo_reference": "CoQBdwAAABivMuE_MO2_bqE2RUVHLKv3FnZaFrGXKZdHZBTfLSMKbpYVca6Mpll3GkiQdunO53IUhkTqzCc07Py0Js2SArRIvWArv6jcFKx3vKL6G4j8CPhpXPTLjKURExS86YONxj6A8qNwu3YY_smWtcTOrXf1Xjd_hXZlQWqFS-fKoddxEhAwcPCvOFig2HJcUsc_tkpQGhTSBhHrO1YD5C7kUlnpq20Y4U5HEw"}], "types": ["point_of_interest", "establishment"], "reference": "CmRRAAAAihN1oCu9xssnuDeYA4iN_R85ADwh8fVCAGieUZbG_WrpNGsx7iKIivgTyWpRod9oqlMqLYWiB3asPq7PAHGvwv8znYY5jmeeZnZlX_eA3qPAtKhDzjRoT-hvPu78eVEJEhBxsmLNZm887Bs7O58ZFyOYGhQYboxVKD99Z799et7yGDbVO4RXBw", "name": "Masters Fine Art Conservation", "rating": 5, "id": "a462c2eef4e22ea319485ae7b84f3d20756cbdd1", "job_title": "Franklin-Retail-Solutions", "place_id": "ChIJp8u2bZvAQIYRbosnWz6cVmY", "address": "1612 W Alabama St, Houston, TX 77006, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.3876169, 29.794149], "type": "Point"}, "properties": {"photos": [], "types": ["art_gallery", "point_of_interest", "establishment"], "reference": "CmRRAAAA3YMEBDH7UCPP4EmroLdxsPAHfoGfpFbUI9AAHtITjcdBMpj5uOukEyxg6ckBp7ZebvsXAhvkACgM9VB6Hwg931tgMd3zEIpkDPTM8rSDzx_2gNZhj_GqDSEROiDbmmgOEhCj77rbmw7bletobgdlJB9UGhTgMaRVtKB8O3caoN10S8Hd5IgsuQ", "name": "Whitten & Proctor Fine Art Conservation", "rating": "NA", "id": "883a8c5ef35ab28e1630235ad65a6b16506a67fa", "job_title": "Franklin-Retail-Solutions", "place_id": "ChIJ8YuXE6K4QIYRn1SF1hazFEw", "address": "1236 Studewood St, Houston, TX 77008, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.3858767, 29.7300997], "type": "Point"}, "properties": {"photos": [], "types": ["point_of_interest", "establishment"], "reference": "CmRSAAAAmpcSdUZbvZfrjrpX5NA91EVKdD7UWy-B6-L9R2ZugwmVzmxk38ynBb-6JDtYF8Z4J4jk-roFY2OBAplcMjLNj6vRT9fe-ehdvM33WE7VdQu1W75z3A5g7OdEkoYwTHuLEhCclrZod5oO2IWvvAKHhAmUGhSD2JTBSxGPiH5U97U2uWxMTDsTgA", "name": "St Mark Fine Arts Conservation", "rating": 5, "id": "ea2d4bac6d74716b33f456dff3aae0cc0b43cca3", "job_title": "Franklin-Retail-Solutions", "place_id": "ChIJKbDEoXm_QIYRcRFBlp0dE8A", "address": "4901 Main St, Houston, TX 77002, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.483218, 29.7482286], "type": "Point"}, "properties": {"photos": [], "types": ["point_of_interest", "establishment"], "reference": "CmRRAAAAFfNaH2jutYx0Z7TzWIoNVVUrNaxLYwZnWngShWpSIFze0EueFAlUCYXYoiiVxNMeDw9bBMs4EZg56Yd5DQClCxSFhMvaeNwwImzxybDjCFjjL8DZBe7pUId4SPSA8r1qEhDr0wSrQK14_OZpIv7LopGbGhTyY4uu2itN5T_EnnjvgFSoVcyUVQ", "name": "The Nature Conservancy", "rating": "NA", "id": "90af6fb9fb926dde9f7103577cebc4150bbb1dec", "job_title": "Franklin-Retail-Solutions", "place_id": "ChIJq-m4EX3AQIYRJkn4Lhccp2E", "address": "1800 Augusta Dr #240, Houston, TX 77057, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.42318089999999, 29.7345943], "type": "Point"}, "properties": {"photos": [{"width": 750, "height": 437, "html_attributions": ["<a href=\"https://maps.google.com/maps/contrib/106788706324997826205/photos\">Erika</a>"], "photo_reference": "CoQBdwAAAFQpQsxIAyHTvgiB-1DzNGS26HVdgFP8pHikfHhWjrIzPf4GbpImpjOFuibT8i-VqGj6SLwb-S5y5-j_bZPQXk2XsSfZqHlLWb4gp9DqZOULXtsjjmh9unlPYLpH9NPFfl0RWiqY2utkO4pZ9Mj990hn2YeryjIlehE4MWpGSQSsEhA2NugIxs74X3ukwwgUvu7SGhS9VPxaiDa45iHMH6mpkSlr_8_2IA"}], "types": ["point_of_interest", "establishment"], "reference": "CmRRAAAApT_dGxEOKxtppqqJF8RoO6h0hNwqKtNshxK7HuflpaLiamdXcTzx9BHKv1jgSlWneuPcT2RezdBBKGhw6mwdwsxspFusTLin1NQKVSQm0NffXlQURHJxfy6aspH8XkFfEhCvmcwZ9VQW796Gax2lBpAcGhQke05zioCCoMtBdqKvYuLxDCuEZA", "name": "Student Conservation Association", "rating": "NA", "id": "1c5ea7722fc0d99e9f7dfca55f5d9078224d51d3", "job_title": "Franklin-Retail-Solutions", "place_id": "ChIJQcqBXfDAQIYRErawO-goGj4", "address": "2990 Richmond Ave Suite #400, Houston, TX 77098, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-96.038102, 30.055621], "type": "Point"}, "properties": {"photos": [{"width": 984, "height": 985, "html_attributions": ["<a href=\"https://maps.google.com/maps/contrib/110279808588468038448/photos\">Peckerwood Garden Conservation Foundation</a>"], "photo_reference": "CoQBdwAAAJ6Un0U_Xq9dKqJeekuhFQELJ0Cx3sUCt6fmfu9XrlHesB32i6DzUVBxusYJgIwys6bzfXpsScC-nMn3_N5PI5LVyxRppUC6gTNEycx5OrwG-ID9j2V0Otg3NXDaTKvBqwXyWq1N6oH_JnkhbB8hMK4n9YmOF-nOgYZmh36pAm8lEhDNggD56JTkIVn21HvczmOCGhQzwVK42fipjOnT0xkpXmdMXDakNQ"}], "types": ["park", "point_of_interest", "establishment"], "reference": "CmRRAAAAv4LR5uKqUdBmzhDUnXjWE_wvgRzZtxUNP8oZ-45Gmg1W_QhV66bMrNvZr2Me0gomaeBb-pfQryoAzUjOO2iCBzlw27Cc--V5-4Tm6Lx25G9KpRWHMizhTl9rO8kalx9UEhB715DkXtmSF5HqGYTYdhHfGhTAUBjH3orP6BwSVmOg-OqTwk5UJg", "name": "Peckerwood Garden Conservation Foundation", "rating": "NA", "id": "e618a4c618cd67ce4f5fdc165f640220ab3b53b2", "job_title": "Franklin-Retail-Solutions", "place_id": "ChIJmUR7pvHKRoYRIIl0o73bPGE", "address": "20559 Fm 359 Rd, Pine Island, TX 77445, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.64386449999999, 29.7515036], "type": "Point"}, "properties": {"photos": [], "types": ["point_of_interest", "establishment"], "reference": "CmRRAAAAnmZ1QcHi8no36BFIAR7zCaK35cehnHpGxDkmXUIxQK0wx936yp85AZPn8mAFB-C-EdrVwAQQWx-9NXZimaLt7iH4B1yWaUSitYgLGRaUpY8vBPKVyVsN39npFSJHWHuJEhCITWXLPKP9ewtE-oMF4gtgGhTPMBmF2CLazm59lb35R1vJBO2GzA", "name": "H2O Conservation Technology", "rating": "NA", "id": "30c07988ef8dfc62dac712b9d587daa4a36f2539", "job_title": "Franklin-Retail-Solutions", "place_id": "ChIJIWZRKeHKQIYRXxta3wOMGGc", "address": "1725 Hwy 6, Houston, TX 77077, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.5705632, 29.7714443], "type": "Point"}, "properties": {"photos": [{"width": 3024, "height": 4032, "html_attributions": ["<a href=\"https://maps.google.com/maps/contrib/108143329814504597326/photos\">State from Jake farm</a>"], "photo_reference": "CoQBdwAAAMDP1_PGf8fXsCDP1hIkscTKB6zHJvegqvV-aBh4DvFEfB8Ipk_Dfa2vx16Fg6Y4fWOAd-Pb676udqCe3w5K51an_VpGqkBttfMMY2uF6ndQsV7DAUX8A5fe2sABCgdQGd-oAmJhPkvLPq6ipWWoglpo5vjOyyaWm8SlxHNC_iL2EhAjx4ZxsdYn2dhd-J_YYAdLGhSn0HipzeCXy-mxCBOkQNRRNR9l7w"}], "types": ["park", "point_of_interest", "establishment"], "reference": "CmRSAAAAcdrT9-KhYKLTMoZnAQzQV28lQesrG7r9nq2BZdw5Bt27rt3p3rOK3GbOfccw1g1xxY32B6j7nFtDtP-nINLAzW6qyUM6GIrsdIvNKxfuKWVp1yeUb-rjp7qewg1-5TbBEhCNUHWk9948KaiNHsTf8sGhGhSr0f6mwPVGc_5HjyKdvoZzaiwUgQ", "name": "Houston Audubon Society", "rating": 5, "id": "050a5458d86bdd1cee7b09678bd6256d0a20a73e", "job_title": "Franklin-Retail-Solutions", "place_id": "ChIJlQOxwVDbQIYR2uX_TZl0TYc", "address": "440 Wilchester Blvd, Houston, TX 77079, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.56820189999999, 29.770778], "type": "Point"}, "properties": {"photos": [{"width": 1800, "height": 1200, "html_attributions": ["<a href=\"https://maps.google.com/maps/contrib/108765250995932379967/photos\">Audubon Docent Guild</a>"], "photo_reference": "CoQBdwAAAIBqKIXjZibmR9uwHKKQUoSOgKwBrW3J1Iv5BsgTZCALr3gxEZd_jTwjszF8RMvSN1ImWNWk2crAyd0hwni_q4IKLy5hzfP0gcQIEUO2hFbfeX2AO3rSLYN543zDCbXEKcG1aUMbLW668tbSJ3iPbue2sRI93x3pPOEXJnUGUvAQEhA5h7TtE0SUmi-wc36tco0KGhSOSYwutZ7moDygt4X-G6F59V8-wQ"}], "types": ["park", "point_of_interest", "establishment"], "reference": "CmRSAAAAC3ePgsu7JwTOEBtiUUBVSqsyZZvaAwctzcFQeYjhd66IpFLPQibASRrPAUrZF__Wtehg5IX9jrvwEqY7odKCsZIsEUvmojs3fJLlwpFmeUM_DhPDg08UJOE9vPZsV7LrEhCL6nn3tCrWXlAjFjWqj2qlGhTx6hrUwet8Z1BwpcUdeN0fCv0H1w", "name": "Audubon Docent Guild", "rating": 5, "id": "7ddd5daf76cc4979e2ba6b062322d1c77d5d1c07", "job_title": "Franklin-Retail-Solutions", "place_id": "ChIJI9XyNFHbQIYRtwHb8EtTpeU", "address": "440 Wilchester Blvd, Houston, TX 77079, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.44932349999999, 29.7803218], "type": "Point"}, "properties": {"photos": [], "types": ["point_of_interest", "establishment"], "reference": "CmRSAAAAUQIgl-tJW2OAAWR029l9I3sWb7_sG_BI_nvgNmec3I8Oagp-o5gTcNN9IUssi4HvOyReN_nNklPHDIl02n3qapHB_sNcqDdNvueHws5N9TUzyYbCoS3oLwkM2M7bWCKHEhAzmYrHtGHcKNRJG6kkP5tTGhSFKdXSQC0HRG_isJbaRizXOz0Qrw", "name": "Coastal Conservation Association-Tx", "rating": 3, "id": "7258b034e119f31e82320bca6e72781ee9f79d75", "job_title": "Natural-Pawz-1", "place_id": "ChIJcekacM_GQIYRPzL13cgQrPk", "address": "6919 Portwest Dr #100, Houston, TX 77024, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.47039, 29.655454], "type": "Point"}, "properties": {"photos": [{"width": 5312, "height": 2988, "html_attributions": ["<a href=\"https://maps.google.com/maps/contrib/101184977609161362375/photos\">aug4</a>"], "photo_reference": "CoQBdwAAAOb_hqZMAcE83LM7E5C1bBT1hLSkHsXZ8ulpum8lonlWWUj4MmDL1ODs2nSglTOmpvh0whzhLqoKUfYDApj-a2B_mTCTaQLsUMtH-sZe-O5tm2f0V6KCOeA_07CDHtJz9sDJLn4ypwjOL6F5HEwEjwvyotBp0sn5Aw2aVda-wGhhEhBP1vuZFPrDu-L7YFGtnqyKGhQTl-OIkQzOek3q6m0X9kFZUH2G-w"}], "types": ["park", "point_of_interest", "establishment"], "reference": "CmRRAAAAmLaI3BeJrC1xuoB8_OMrvTKU81-lUWz2ZhAnBEjdzQ1jfzZf0Rm6IedF4iFBjyybSOlHes1CO5YzdbH1Lzubs0ZGn2689vu84LT2zYqwPTyqXFqkf2gxK5DZnQDRHrLgEhCSmTQJobAaV1K526ZS3iuqGhTmFHpnCOlYDqMSz7bIIjhn9ME9sA", "name": "Willow Waterhole Greenspace", "rating": 4.3, "id": "0127506e8071350c2d48f0ca56e939045297a0f4", "job_title": "Natural-Pawz-1", "place_id": "ChIJR6_2zTzqQIYRsA7wExgfDWs", "address": "S Willow Dr, Houston, TX 77035, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.4003322, 29.7388505], "type": "Point"}, "properties": {"photos": [{"width": 1136, "height": 640, "html_attributions": ["<a href=\"https://maps.google.com/maps/contrib/117056878997299689379/photos\">Marisol Brown</a>"], "photo_reference": "CoQBdwAAADIfVuIPcA8-DklKEdkaPClT6Ny0904rGcUFniI2Cl1mWQBS2S0VV7rCoWegZbGpWYKWMnblWcstwH9YNdac-mevoBtOl0DaPpKMJ7S1jmkxO_MZu3qUPCNsELakjrOK66V--yALv6lB8NfKPTROw1BJoedmk03Y_VPu_641UVFSEhBV3jfgOU1YS4urgcTaFmuFGhTX-icRbAHrmD7Vti_ngG2Z1_VPRA"}], "types": ["point_of_interest", "establishment"], "reference": "CmRRAAAALlcvN7x2Fol1MdyOoV7Tx3b81wlUdEJppoDFBBkPTiVk4LH3kbKDzqp4zAZMXK6wVuJLrS2leprV9QMXklJCn4p_IpRKoAA3TxXC4n-Dm1rY-tWGssqGwx6cDppE7qktEhAn4gd3z1t439KLSy-7nw6CGhS18OzFf5PNhHunCbwr4HvqqHOkXQ", "name": "Masters Fine Art Conservation", "rating": 5, "id": "a462c2eef4e22ea319485ae7b84f3d20756cbdd1", "job_title": "Natural-Pawz-1", "place_id": "ChIJp8u2bZvAQIYRbosnWz6cVmY", "address": "1612 W Alabama St, Houston, TX 77006, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.3876169, 29.794149], "type": "Point"}, "properties": {"photos": [], "types": ["art_gallery", "point_of_interest", "establishment"], "reference": "CmRRAAAA_HLZ2Jvohn1kuhKZDjivXPSeJouDnlq4CHFhov17a_dc1MoHeM7M6B2a8ReJCHo-w2m77KR3KLnuWr_Y6qIdL_DhUFGq2BHefDHvKgtBfRWWgVvEBb1vbbYtM8wjrffcEhAuKcPRub9plcWN8rGozXYmGhRH_y7tASjA_N8YAPm_REKHqiFQyg", "name": "Whitten & Proctor Fine Art Conservation", "rating": "NA", "id": "883a8c5ef35ab28e1630235ad65a6b16506a67fa", "job_title": "Natural-Pawz-1", "place_id": "ChIJ8YuXE6K4QIYRn1SF1hazFEw", "address": "1236 Studewood St, Houston, TX 77008, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.3858767, 29.7300997], "type": "Point"}, "properties": {"photos": [], "types": ["point_of_interest", "establishment"], "reference": "CmRSAAAAGq-F2m9ZMSTw0BEGXz_p-nAIbcj8RczL1FUUmetCZSYXgS1kOTvp3_aEONRRJBl8UGGrUKSljbO-q3AndjdowZCSURyckAOhiXBtOOGxFYnXNnW_ZluKDL29nGThPJsTEhCUFr3xE9KPC6sJ_nTdMJ96GhTmzoBzCZABVZHjLl4METGqHU_JkA", "name": "St Mark Fine Arts Conservation", "rating": 5, "id": "ea2d4bac6d74716b33f456dff3aae0cc0b43cca3", "job_title": "Natural-Pawz-1", "place_id": "ChIJKbDEoXm_QIYRcRFBlp0dE8A", "address": "4901 Main St, Houston, TX 77002, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.483218, 29.7482286], "type": "Point"}, "properties": {"photos": [], "types": ["point_of_interest", "establishment"], "reference": "CmRRAAAAoeE-6nksCb7sOr_YHJCRsZpgolaYavyIw3XT_X9Hm7FTwfJLkx-dRch49QWaNAJYQBOiX8YradPh3hBhNzo7tjtAwhxf56Fr659I1FnV0xa8euW51hsnIL1qAuiKv5vxEhAjVj9JtzMLKgZNeXztY0I7GhRkjGJqsltFjqUXtAhVOLMLXUnFFA", "name": "The Nature Conservancy", "rating": "NA", "id": "90af6fb9fb926dde9f7103577cebc4150bbb1dec", "job_title": "Natural-Pawz-1", "place_id": "ChIJq-m4EX3AQIYRJkn4Lhccp2E", "address": "1800 Augusta Dr #240, Houston, TX 77057, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.42318089999999, 29.7345943], "type": "Point"}, "properties": {"photos": [{"width": 750, "height": 437, "html_attributions": ["<a href=\"https://maps.google.com/maps/contrib/106788706324997826205/photos\">Erika</a>"], "photo_reference": "CoQBdwAAAAMJFCgMBsN7zcpQfk1bQh0TEayW-BmCppzt4Pw_k2Ad2W-3vtfcMhd9_EG9fZ85yFZkyxERFxQ2j5Jpkgl_I9oRnNOslt0iKngOx4hbWItAuGlpiYSbuN4A3R_SezdJqXi93xytA7zy99mAUPoi-mkSatwJGMVm9HctBydWnMzSEhDZk1IhabMGSUCtmasqIJ5ZGhRXADyu_DDIXdKLxlhWszCBiOhFdQ"}], "types": ["point_of_interest", "establishment"], "reference": "CmRRAAAAPNz3mQkVOr7UvkF86JSfX2stQqzwFG8GWHhHulHu9xc_lFc3rvrXph8EtESlvbI8qBCazDGUb8Uh9DPnjwIQ5zsxOJpvR2TKONB0q16773fUa1WIBqSR4ZQwFbW9_-kTEhBLB45VvnQMciY4OWcn4JgkGhT2LPhMbo92EtVA_zaLw74UIl9oCQ", "name": "Student Conservation Association", "rating": "NA", "id": "1c5ea7722fc0d99e9f7dfca55f5d9078224d51d3", "job_title": "Natural-Pawz-1", "place_id": "ChIJQcqBXfDAQIYRErawO-goGj4", "address": "2990 Richmond Ave Suite #400, Houston, TX 77098, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-96.038102, 30.055621], "type": "Point"}, "properties": {"photos": [{"width": 984, "height": 985, "html_attributions": ["<a href=\"https://maps.google.com/maps/contrib/110279808588468038448/photos\">Peckerwood Garden Conservation Foundation</a>"], "photo_reference": "CoQBdwAAACqvHwHbYvGydAwvXPdIa4ZbCcnUV-mSj01EEvdsLkphoMh9ak1iZSUdALG8yF8k7L1k8Og-cZeXATAhKg6i1lb6uJTgqHOCSodLHpLz-SVqetI86vUwDjPXYVrXfSgSE0RQwU4yO46Xz0X-IvFhH-pr8O33pGAWaVeRgk77sWYbEhAcjBA9x8I83Encp7uWuPi9GhQN_8kLo_2xPaiIxXXUskhxGhry6g"}], "types": ["park", "point_of_interest", "establishment"], "reference": "CmRRAAAAch15RoP0auATpOKNEQH4pnsVbKGnXPryNYnkUkRFAmzdmoYyFpba58qWrnKf150OaaPz3dhI4LQgDPTsek6VNIxcOAv3Ongu93N9PP-GiCo3k5RQbTFLsuAEx0-jSIb8EhCwganKrNFJTtVh_OGiU-J5GhTwhTknVh5yjgJ3VeBbybFzxr4PVQ", "name": "Peckerwood Garden Conservation Foundation", "rating": "NA", "id": "e618a4c618cd67ce4f5fdc165f640220ab3b53b2", "job_title": "Natural-Pawz-1", "place_id": "ChIJmUR7pvHKRoYRIIl0o73bPGE", "address": "20559 Fm 359 Rd, Pine Island, TX 77445, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.64386449999999, 29.7515036], "type": "Point"}, "properties": {"photos": [], "types": ["point_of_interest", "establishment"], "reference": "CmRRAAAAcTSpBlUwlRQkizu6dcbRiSy_LF2ZwHlilMKmeeS4_9vpT5ccD7KzeFd8qsbDr6RhOzHsgOJbWNY1tNuHPiZEJSDl3si_ya6v_lRmAkMBHnG8iMIqjS1areSD45AF10ONEhCkm6fieQR_o5oP5qO8azg3GhSMxwcNRJChpORHPu7ruhxdP09rOg", "name": "H2O Conservation Technology", "rating": "NA", "id": "30c07988ef8dfc62dac712b9d587daa4a36f2539", "job_title": "Natural-Pawz-1", "place_id": "ChIJIWZRKeHKQIYRXxta3wOMGGc", "address": "1725 Hwy 6, Houston, TX 77077, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.5705632, 29.7714443], "type": "Point"}, "properties": {"photos": [{"width": 3024, "height": 4032, "html_attributions": ["<a href=\"https://maps.google.com/maps/contrib/108143329814504597326/photos\">State from Jake farm</a>"], "photo_reference": "CoQBdwAAAMNj-QSPgM9Jtd8n-_Lh2aNfRWWUecCUbc9KeM55-9GTNOs6kDfjgCwPF5PWNNeBGVEThDUIV53RQxy9Ft4l-mhqo--RtoRs5LXuX00wmj6uNuhcxHGLxELGQmclgCdofm_wsCuLkI5WGPo6AkDeeCGho__W8zrhCkmlnashQUOwEhCX9bws3-togOEKVTPCExwyGhRvLPXzWm3DJI0SW3KPYytBhqaZyg"}], "types": ["park", "point_of_interest", "establishment"], "reference": "CmRSAAAAqIi1CZSwYzpZVPzih88rjh9b-9CTyQb9r1I3wUt3LOl0c_s1KQ1K8xrbTI21Kss6HwXSOg5Mkk2HOOMSEVbfSJFsUHGEopDUlkmGjX38ndzc9uUbEVxmpztWDoJjjWhXEhA2_I_PKCy2R_zqP2acwKEDGhTXszHDRNpl9W0Ff8WS4Q0jmMsBuA", "name": "Houston Audubon Society", "rating": 5, "id": "050a5458d86bdd1cee7b09678bd6256d0a20a73e", "job_title": "Natural-Pawz-1", "place_id": "ChIJlQOxwVDbQIYR2uX_TZl0TYc", "address": "440 Wilchester Blvd, Houston, TX 77079, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.56820189999999, 29.770778], "type": "Point"}, "properties": {"photos": [{"width": 1800, "height": 1200, "html_attributions": ["<a href=\"https://maps.google.com/maps/contrib/108765250995932379967/photos\">Audubon Docent Guild</a>"], "photo_reference": "CoQBdwAAAM8FTeYXi6MuBpvvy8AM9xJT4hzwYjSSTlwuyfmrd5US4mnfaHSsi9TgsdV807QbsDIN8G-sZwobzaMpCsWQAZ_I58Po8_HHVVTiTZ9eLMG6nkyfR42byMYZot5G1w_FuQJFycXtK6XVSOMUkUJAxuZRspqOsnq-IJmiTIrVkPXCEhA9OgsMSuQLx8jAh93ttduaGhSyiD4GPjTzOI6Fzs8Rxjox-2T48g"}], "types": ["park", "point_of_interest", "establishment"], "reference": "CmRSAAAAaBCiZnGk1gAP7nYhDxUIBD9-pZ54-9OgGPbHYl6qo984z4-OBo8V1aNgulkWGUum2aQZdpFEI821K28BP8pyFOrgaz4P_4Y2dd2Lv6RCYy_RrImARxH81udtIgs67TpXEhBU8yRFSf4axEfMHIYt1zQPGhT5RxJ9CWI83sxHsssWwWFIwvTP3g", "name": "Audubon Docent Guild", "rating": 5, "id": "7ddd5daf76cc4979e2ba6b062322d1c77d5d1c07", "job_title": "Natural-Pawz-1", "place_id": "ChIJI9XyNFHbQIYRtwHb8EtTpeU", "address": "440 Wilchester Blvd, Houston, TX 77079, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.44932349999999, 29.7803218], "type": "Point"}, "properties": {"photos": [], "types": ["point_of_interest", "establishment"], "reference": "CmRSAAAA1OTX-1PakdQKYafdl7jnsG59Dtd5XjRbscbeTgxh1crbQc8MlrsFYaAQ0COo_EcG88tMGkvjy1TVN5c1A7CQEyeUkhh2neVKhwBEktVIHUwFznCrelBVsCwnLsrKbJxREhAbrB8AOXdWV5qY93swpRHDGhSj0QjstN4N89urDil_lu14O7E5KA", "name": "Coastal Conservation Association-Tx", "rating": 3, "id": "7258b034e119f31e82320bca6e72781ee9f79d75", "job_title": "Luxottica", "place_id": "ChIJcekacM_GQIYRPzL13cgQrPk", "address": "6919 Portwest Dr #100, Houston, TX 77024, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.47039, 29.655454], "type": "Point"}, "properties": {"photos": [{"width": 5312, "height": 2988, "html_attributions": ["<a href=\"https://maps.google.com/maps/contrib/101184977609161362375/photos\">aug4</a>"], "photo_reference": "CoQBdwAAAGO_xXr9Fb5unfGlujC9Q5L4JQIfRibBLnH7QazPYwE7VV9wLteiWSux1AJeE8CE28FPM4cMpc9ArQfmrufMKQGGNGonXO3oiPwntkgjfbetUvA4TL4BJde5mpXX-ti-Cbsd91ZiRs4G_GjD_Dc7LxFRoAVnb8vwgGRdr9d55Hk6EhABCXWeB95KF_3ASMpZqa_cGhQvJ4pIFl-3Cw7G2eto4mq4lp-qBg"}], "types": ["park", "point_of_interest", "establishment"], "reference": "CmRRAAAAy7wH8wk5NA9zA8ELm64wFJ5VxzYLtEcJLx0jSyBmg7eyhEmF62VoTU7XJPDgHlRRQS59_Nhc89dzEkYRwSY6bCp9CDT5HpKQfN_cHpoDf16cmOQkQGi3jiXE3InWDUVJEhAvMwpk8dLz31c87jn523OKGhS_vvKH-IDXaKRU3xtlDZtQFQGKOQ", "name": "Willow Waterhole Greenspace", "rating": 4.3, "id": "0127506e8071350c2d48f0ca56e939045297a0f4", "job_title": "Luxottica", "place_id": "ChIJR6_2zTzqQIYRsA7wExgfDWs", "address": "S Willow Dr, Houston, TX 77035, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.4003322, 29.7388505], "type": "Point"}, "properties": {"photos": [{"width": 1136, "height": 640, "html_attributions": ["<a href=\"https://maps.google.com/maps/contrib/117056878997299689379/photos\">Marisol Brown</a>"], "photo_reference": "CoQBdwAAAJnNMK5OL3qgB7p0JOtc5t_YS16-qb1cXQWYr_msQBvzauqxBOMNQjh5GFiekZ69ZyEQtDyiyv8Gxh3RaJdlBt2EGWJ3flATHKFa5w9-hj3RcpFUktNL8SDxz1mbUAKwl7g878Namjp-l8Ub16rffGNzMr5jA4RutmSWrxLw2p9rEhDzk3AuhfzYfYegEbW-IW2iGhSeGtsHV66oZ-tP4rl6On6zGs9xsQ"}], "types": ["point_of_interest", "establishment"], "reference": "CmRRAAAAbp7hQHzw8yIJ0K3rx3RKjrUVMC5-mlPgCAB0SFmoS8bhbc6T-BURPjMHXVjPe37ySvBHsbHV3wgMKR5IuXQg6lpw1tOiBsZkHmYB-4CPMPS2v_cTXj2v5V6pTesx4zP3EhA0dIxCN3_7Pl4etyMEq4UUGhSJX2z6hbGWoraU14p63s73RsTAKg", "name": "Masters Fine Art Conservation", "rating": 5, "id": "a462c2eef4e22ea319485ae7b84f3d20756cbdd1", "job_title": "Luxottica", "place_id": "ChIJp8u2bZvAQIYRbosnWz6cVmY", "address": "1612 W Alabama St, Houston, TX 77006, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.3876169, 29.794149], "type": "Point"}, "properties": {"photos": [], "types": ["art_gallery", "point_of_interest", "establishment"], "reference": "CmRRAAAAG7s8VSITpVHiPQfDXGSqfotiA8DISeeqtMQ-bSQskgzeSG6GoJ504_BPM7mGSvil9h3H2EWNwK0_kaCspEc7qsOaXY-z2LSoQDeZEZqEv_r33f23nSZE6IDYo5eOEQJGEhDY40dRZEd_4sqhSgiGj23WGhRLqruMjmBlgxjdT3YZxtuwRGNr_w", "name": "Whitten & Proctor Fine Art Conservation", "rating": "NA", "id": "883a8c5ef35ab28e1630235ad65a6b16506a67fa", "job_title": "Luxottica", "place_id": "ChIJ8YuXE6K4QIYRn1SF1hazFEw", "address": "1236 Studewood St, Houston, TX 77008, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.3858767, 29.7300997], "type": "Point"}, "properties": {"photos": [], "types": ["point_of_interest", "establishment"], "reference": "CmRSAAAAf_NDWnlS7WGs_vB8TMnD730Ei_TQIoGZ3EnOvhu6pG5eiin6tPRIvFBwKP0WQRCLS4CX86IqL_gmHKHcnSeNuEEfXCXFo8fVgrTpBUoQuaJ5jZOv9MMtRm-lhZDZrlU2EhCa2Ur7hvBfT2kEa0qeThPbGhRSuHl4lvU08Uc735xAoR9NqfM0xw", "name": "St Mark Fine Arts Conservation", "rating": 5, "id": "ea2d4bac6d74716b33f456dff3aae0cc0b43cca3", "job_title": "Luxottica", "place_id": "ChIJKbDEoXm_QIYRcRFBlp0dE8A", "address": "4901 Main St, Houston, TX 77002, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.483218, 29.7482286], "type": "Point"}, "properties": {"photos": [], "types": ["point_of_interest", "establishment"], "reference": "CmRRAAAA4gn3PDkOf8zSPy5-drMwvrk9YbhoyIgei_Q5TIGesmgTlSOh53RgZfsobclCWF8igFsE2uPDtYGbpjHBuD_tdUAFOrd7mzo4apv6QjNHOsj9ZWYvpDUFscA-Qk20X0G8EhAtt3T0JLwIeoYLf0gVZaw3GhR6502EZL84Tc1Eb66GRiNA6bgk-Q", "name": "The Nature Conservancy", "rating": "NA", "id": "90af6fb9fb926dde9f7103577cebc4150bbb1dec", "job_title": "Luxottica", "place_id": "ChIJq-m4EX3AQIYRJkn4Lhccp2E", "address": "1800 Augusta Dr #240, Houston, TX 77057, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.42318089999999, 29.7345943], "type": "Point"}, "properties": {"photos": [{"width": 750, "height": 437, "html_attributions": ["<a href=\"https://maps.google.com/maps/contrib/106788706324997826205/photos\">Erika</a>"], "photo_reference": "CoQBdwAAAFi8GpMbQHkaPB2-5MUnAxkfwGl15r9JJNavKyi0ocLtSN0dpVbMzLuQhN88L3HKB1fVgYfQBgDCeMs-9q1djqe9a1TeIVu7mDOsT9idye25f94vg2aiO7ISWV7VLEYzSjhze46knPE8DZha4WFIvcBl_OZraM1yw6vU0rL-En5AEhDzINMuDckY0NWpYheDOq7qGhQT2HqsxFOMGQmCDI-2-r0EbZoXhQ"}], "types": ["point_of_interest", "establishment"], "reference": "CmRRAAAAz-L5hOLQxi1zuksZhKkDHscpWA8gl5F6xu_XRl7BHH1LSgRF4CtVanMZWa-E9IAAckg5Yy-wdtiR_LEX39l2LkAmABYLOGIpdEWKIYzLHYOMjsJr32HGck0WRt40MTLxEhD2_rFaGMCwjfO5jBJ7XbDMGhSY9DNrNW9tGWdyuxJ1bYKsQ4IWVQ", "name": "Student Conservation Association", "rating": "NA", "id": "1c5ea7722fc0d99e9f7dfca55f5d9078224d51d3", "job_title": "Luxottica", "place_id": "ChIJQcqBXfDAQIYRErawO-goGj4", "address": "2990 Richmond Ave Suite #400, Houston, TX 77098, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-96.038102, 30.055621], "type": "Point"}, "properties": {"photos": [{"width": 984, "height": 985, "html_attributions": ["<a href=\"https://maps.google.com/maps/contrib/110279808588468038448/photos\">Peckerwood Garden Conservation Foundation</a>"], "photo_reference": "CoQBdwAAAIXvkziqQY3meRveGN0NJWNurfXLZ43wJdutmglh9cMdac7CUOsXtL4ClaAMNlBjjvZIg4ATxqIOHOndSm6GeNmFNKrx3yr1nwtNbcl0UbTmhECH4Oo6ameEBo1Rl5NbKELbeTsWgem41LlhOkXBuQvmtsehZX36VsdRSIbX8ir5EhCTDg7YjNKpW5EOI2ksZpiaGhSjfOZ8xj3ex63ARHgHcOu7Cn94Kg"}], "types": ["park", "point_of_interest", "establishment"], "reference": "CmRRAAAA5K5egH8ro_uoqQNiwZ6HrngfG_kLcP7ni8uZxxb4m7TWKKgoLY103ifPcjJhmxoIvRRGp57IDjIxnW0sdrV-g3Dngh5qxk9hrTNaC2SyEUEUW8Dou0_4flqm5upJva-1EhD1ASCvt8uWRngrux9wUDw3GhQuN6nlDkrcd3QqWM3ObQ2No2jzSw", "name": "Peckerwood Garden Conservation Foundation", "rating": "NA", "id": "e618a4c618cd67ce4f5fdc165f640220ab3b53b2", "job_title": "Luxottica", "place_id": "ChIJmUR7pvHKRoYRIIl0o73bPGE", "address": "20559 Fm 359 Rd, Pine Island, TX 77445, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.64386449999999, 29.7515036], "type": "Point"}, "properties": {"photos": [], "types": ["point_of_interest", "establishment"], "reference": "CmRRAAAANw-U64hRRlUu7KC0NcFtSdgTRt1muZmxT-_tn8_zZTRPYunPxyWZUq2-cWVaUDZ_SlHj-b01q0H7iLsmHjx8PPn_Ncsxxtm9n_aY3Z2ntq--ol940uX0JqD51dxEliZ8EhApLAANZwtXwvkqAq1UwqGzGhRijy1PvRBq-Ql190Rn-pG5pJ8zRQ", "name": "H2O Conservation Technology", "rating": "NA", "id": "30c07988ef8dfc62dac712b9d587daa4a36f2539", "job_title": "Luxottica", "place_id": "ChIJIWZRKeHKQIYRXxta3wOMGGc", "address": "1725 Hwy 6, Houston, TX 77077, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.5705632, 29.7714443], "type": "Point"}, "properties": {"photos": [{"width": 3024, "height": 4032, "html_attributions": ["<a href=\"https://maps.google.com/maps/contrib/108143329814504597326/photos\">State from Jake farm</a>"], "photo_reference": "CoQBdwAAABMKE3zmSrDYtdxrGmgWjMWEjP5SarbTvb8bWYQ0eUGE9Qe4lLjHtgUpPD0_MSKUR0YChP8tcgFZxVXiUypuLbrFC2AyXkNP3xK3OaKR204djLDIH8g1pISTRaPq3DeJH6lONCWgvrXDVi3okfrqUWkVSLi_kY2QQt2xxDY6nKD6EhCghXKOxInt_cQrfH_s1RyCGhQfk-roYPTqObolfhF9dQ6txCK_kw"}], "types": ["park", "point_of_interest", "establishment"], "reference": "CmRSAAAAPnMuaBLKi3fSNb8DeAoF-ShfuK9X6L9urpmL9fqh6qPvW636g4PlZaz3Fi5B8VRV65FpbNdYqoLl_hQY31JhLHh-nnuVVY9vM2VcowRa5rngZqcXcNpJkY1mVBeVkr5FEhD13yQddqiUUYoiZd2IQeHUGhS_WxJnkyWuUut9bKeb9NJfgGJUDQ", "name": "Houston Audubon Society", "rating": 5, "id": "050a5458d86bdd1cee7b09678bd6256d0a20a73e", "job_title": "Luxottica", "place_id": "ChIJlQOxwVDbQIYR2uX_TZl0TYc", "address": "440 Wilchester Blvd, Houston, TX 77079, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.56820189999999, 29.770778], "type": "Point"}, "properties": {"photos": [{"width": 1800, "height": 1200, "html_attributions": ["<a href=\"https://maps.google.com/maps/contrib/108765250995932379967/photos\">Audubon Docent Guild</a>"], "photo_reference": "CoQBdwAAAC085J0cf4keD9LXSPi82unYa-3-ej7y5vpLqe-meLjwiaRyBTi0gZF1nXahRoun-8_Cbb6Vn_I9HTrw0p9a6lncxYyrVug_PzWaInA-UWhFWcGnJAAwnIcqUTyhAGkYUmKArR9tjeUooum6Dsl0HbIxcJQnV5Q7-olZ3AvQqZfQEhDZwTCh0rOIBlJHBXR-G2MkGhTPXa4QtEl31cMfF335O-w7rbVAIg"}], "types": ["park", "point_of_interest", "establishment"], "reference": "CmRSAAAAFzyWJjEesNNgTUeROdDdyCwioXncQYBVYeVIvjJbX_gCZe8YfHdX3b0mlbGpyKvgyKmeg_ewRGRTpZebriSnHHdR75JR19NwKlVn3CTchQ0tlXTN_Y9LPl-8AiqKD5AWEhCMg1mJiYojIrBx1XbmMBukGhQvbdTiYlhV73elZtHn-02o81ICoQ", "name": "Audubon Docent Guild", "rating": 5, "id": "7ddd5daf76cc4979e2ba6b062322d1c77d5d1c07", "job_title": "Luxottica", "place_id": "ChIJI9XyNFHbQIYRtwHb8EtTpeU", "address": "440 Wilchester Blvd, Houston, TX 77079, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.44932349999999, 29.7803218], "type": "Point"}, "properties": {"photos": [], "types": ["point_of_interest", "establishment"], "reference": "CmRSAAAATG7p1Cl2vzco7XHfZZ9FZT99GoqrQjoqX4o3981V5-NG3tCDQaQ3B1JN8puv9SG6sOP5x3Mbt4Ahv9754AR9Wzoc4unE0i3liPuay34mYA6P9nViQX7othG5XoYtxkfVEhAx6kpJFywpxEDLYC_7zKVzGhTk1bOkfWJBswzfdxHTTFBaOJOcjA", "name": "Coastal Conservation Association-Tx", "rating": 3, "id": "7258b034e119f31e82320bca6e72781ee9f79d75", "job_title": "UnitedHealth-Group", "place_id": "ChIJcekacM_GQIYRPzL13cgQrPk", "address": "6919 Portwest Dr #100, Houston, TX 77024, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.47039, 29.655454], "type": "Point"}, "properties": {"photos": [{"width": 5312, "height": 2988, "html_attributions": ["<a href=\"https://maps.google.com/maps/contrib/101184977609161362375/photos\">aug4</a>"], "photo_reference": "CoQBdwAAAJnm0bjqNoA6giOX21_k3QyRPlhX0DGqmxSFTafaCuO57A7P_b72vfQL6vnkD0TPexCAWo9b3jGcGLryD5d973OVpAlV9b3skT_WXfBCbxEsBJ90JPjk60oJdQnYhCNO7y4pqjee-aZPIFe7-OQR1V_fKnQ5LbnD-mceOzdQd2znEhCCAJbUOJgy1fnKOH0NY-v5GhS72ftpMHLFha7jmjbh-nedyauH6w"}], "types": ["park", "point_of_interest", "establishment"], "reference": "CmRRAAAAlaQyVMBRdF0NIpnx8vUkKWWsyXub8c1xNvHFTnTpTKzf-RGIob3D3RMP7KEmL7bl0OhvkQNU2FoB494osI77xPcOKxC98Z0s0zAfOU5q_oRTYwg6kVVyRRL3RCRleW4qEhAKU3m4h0V2wW0MgDCTMOlJGhQZlC7qyzuiDrH8fxhw1QjBvXRETQ", "name": "Willow Waterhole Greenspace", "rating": 4.3, "id": "0127506e8071350c2d48f0ca56e939045297a0f4", "job_title": "UnitedHealth-Group", "place_id": "ChIJR6_2zTzqQIYRsA7wExgfDWs", "address": "S Willow Dr, Houston, TX 77035, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.4003322, 29.7388505], "type": "Point"}, "properties": {"photos": [{"width": 1136, "height": 640, "html_attributions": ["<a href=\"https://maps.google.com/maps/contrib/117056878997299689379/photos\">Marisol Brown</a>"], "photo_reference": "CoQBdwAAAGBxVYXEJ467UNDatOJbvhqyYACROSd14rqYW0clowFbcD8lXRhPGj_L1wC0jF1hJMkZncSRw8nERrwu16dse2U59-EwZxQsHC24roeYOOeK9tYncvGtAL82nLuHYI-kxe_SAZ6ovcP7L4o50Q3gW9-D_PmaM3ga-ZHW6Wh3Ut5aEhBysiAbKRpJ4L96s0hGIth2GhR--am0eksELtdngBRuok5SUsSnfQ"}], "types": ["point_of_interest", "establishment"], "reference": "CmRRAAAAm8U1W9VecdQYOK4lOKYpNEFrsK3sAlnIrDGxiKB_MDuy-vyl_4I4GL2jOHb2DbiKlRfz6x0PvboZt-pzAjrfXOPu89rjunqiNFjvYRoEAiIuWcyd3_DjdVHzwvSKC5bQEhDGvl1pS6LH7TP8neKxKIcEGhRLgVQdIqEcJkoMHNytAoYzDOIBbQ", "name": "Masters Fine Art Conservation", "rating": 5, "id": "a462c2eef4e22ea319485ae7b84f3d20756cbdd1", "job_title": "UnitedHealth-Group", "place_id": "ChIJp8u2bZvAQIYRbosnWz6cVmY", "address": "1612 W Alabama St, Houston, TX 77006, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.3876169, 29.794149], "type": "Point"}, "properties": {"photos": [], "types": ["art_gallery", "point_of_interest", "establishment"], "reference": "CmRRAAAAwRMvnTvQTeJvhPsBdzvxUTWgB3Wis-Tg54ihb7JxGk7ho-QBINyhgGyBq1PBznit3un_S7FD3r_Kqy2ppsCU7pmjgBtgglov7O7QVgbvQWJwIbFk-_WeSjTDH-iPDUUmEhDSnXY20-Vh3Yzbup8YHLX7GhQRuBjZ3D7W2AtoMmL6ckLHMVNNQw", "name": "Whitten & Proctor Fine Art Conservation", "rating": "NA", "id": "883a8c5ef35ab28e1630235ad65a6b16506a67fa", "job_title": "UnitedHealth-Group", "place_id": "ChIJ8YuXE6K4QIYRn1SF1hazFEw", "address": "1236 Studewood St, Houston, TX 77008, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.3858767, 29.7300997], "type": "Point"}, "properties": {"photos": [], "types": ["point_of_interest", "establishment"], "reference": "CmRSAAAAgx4IfvVWhUsQIdgtQVWw1HjXtW32JqgFeXDxDuZvhFcZIR1u5V4sMYarY-LJL0cFlloe_-TNeKopIkGcY12WJvWien_GXiJGxFEp432GaWupxEp2zFcF8rD0f5jSsHRzEhAIMPpIawr4EyESQSyMAWTMGhTpF_gBAwVn6urD9NV7JQghv7Pluw", "name": "St Mark Fine Arts Conservation", "rating": 5, "id": "ea2d4bac6d74716b33f456dff3aae0cc0b43cca3", "job_title": "UnitedHealth-Group", "place_id": "ChIJKbDEoXm_QIYRcRFBlp0dE8A", "address": "4901 Main St, Houston, TX 77002, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.483218, 29.7482286], "type": "Point"}, "properties": {"photos": [], "types": ["point_of_interest", "establishment"], "reference": "CmRRAAAAmEivTH3ILploAoVXgDHeQAhKfwBfyE7j4QuGSMR0k6oKG_DhFdGD2-lEDvdz9nolyuQYoAQFrXHxYDZESh2MmLCMaRm8Bj6FeNA1qQEZZQlFtu_ovsIH1zKzYTpO1iHQEhANDTch8ddaB7TkMwSWoonbGhSXMOMPdIF-VW0rmckR4ILK91Hqtw", "name": "The Nature Conservancy", "rating": "NA", "id": "90af6fb9fb926dde9f7103577cebc4150bbb1dec", "job_title": "UnitedHealth-Group", "place_id": "ChIJq-m4EX3AQIYRJkn4Lhccp2E", "address": "1800 Augusta Dr #240, Houston, TX 77057, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.42318089999999, 29.7345943], "type": "Point"}, "properties": {"photos": [{"width": 750, "height": 437, "html_attributions": ["<a href=\"https://maps.google.com/maps/contrib/106788706324997826205/photos\">Erika</a>"], "photo_reference": "CoQBdwAAANPz_qPZ9EA5t5atwUP5nSW5wqY_3Q9a7M_z2bl5fizJfuxxrkm-Z3pny8X8sHsqnWi30FPK0Xjj7Umt1MGbw4nx2RlCP8qkm3Yh95WKbaXcmXYU7h6alfWvuXPCFVWwlSFez4Ku78UTigIK6A-RjhdlKLDc_L3h0DVaYW9JLzoREhC7u_IpY9JEAuu8urQmfFTwGhR45wDfyQg7_ho-OA76UJNQH9k02A"}], "types": ["point_of_interest", "establishment"], "reference": "CmRRAAAA8AvqMooY7EqD8utq--qP5veIw4Mov_UCZqHyxpkahFE3T4gW_7JOSucyxOLIEm9MuAblqaBA-a9xqYvHxZduVfhLBAlk7ajvtH4gmJa9DXm3uKO9fzAMX4yJfjj4V2v_EhAEM4w-XvE6DIB_sUtLJLbsGhT0vwTHEzZvETP4yBAsQKJH5P_ynw", "name": "Student Conservation Association", "rating": "NA", "id": "1c5ea7722fc0d99e9f7dfca55f5d9078224d51d3", "job_title": "UnitedHealth-Group", "place_id": "ChIJQcqBXfDAQIYRErawO-goGj4", "address": "2990 Richmond Ave Suite #400, Houston, TX 77098, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-96.038102, 30.055621], "type": "Point"}, "properties": {"photos": [{"width": 984, "height": 985, "html_attributions": ["<a href=\"https://maps.google.com/maps/contrib/110279808588468038448/photos\">Peckerwood Garden Conservation Foundation</a>"], "photo_reference": "CoQBdwAAAHOIyJPjuMQGIh9ZFac0QlMd0224D9Zmm6-Whavbgv_TesP8Lsoyl5gQ88FudHtOkdT3Oqx40qw19XEmBMPSjtyu4QvdM8azcycbKPulUcpMrOpG0q3Hm9okfqxKVaEpfOKYswmN2rNt2QFOoWG6woiceZvRi80VAoLcnpotB6UCEhBIPTU5-rb6ul4OHBtMTXuUGhTYRWJMNLZWrqhWIdjOgtlHbhmQgA"}], "types": ["park", "point_of_interest", "establishment"], "reference": "CmRRAAAA-j_fz3M1_W6AJHTZZbZRrj6bkBGfK1Dm5ZfiFP8fxbQQQvga7dxGXKSR9tD616o6YqViW4PRGHPd0gFW3QXjcUa7PseDHyejPBFVlKUlWjSZmy9HWWmqONxXJ4m2it6sEhAA0vUyoQJc62ihb-2Y6QbdGhR1Tqxt04NG98aR4gG5CiEIJclykQ", "name": "Peckerwood Garden Conservation Foundation", "rating": "NA", "id": "e618a4c618cd67ce4f5fdc165f640220ab3b53b2", "job_title": "UnitedHealth-Group", "place_id": "ChIJmUR7pvHKRoYRIIl0o73bPGE", "address": "20559 Fm 359 Rd, Pine Island, TX 77445, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.64386449999999, 29.7515036], "type": "Point"}, "properties": {"photos": [], "types": ["point_of_interest", "establishment"], "reference": "CmRRAAAAjXSTL3KXFI2AEofwuRQVuaraGxrAz7VRGeuUJJweTtX84F7KXw-k4hgb58iTT-xcbjb8QGlYUBN3FaYE2PT8HNKrgYW9ZRl08l5WwzwBSexhOAY0OCj_kt6PA-Ie9RZGEhCxvl8sqRIWCNkHNiEmpKzSGhQycQrZyidZhdXXLQ-XbcvaJqUN5Q", "name": "H2O Conservation Technology", "rating": "NA", "id": "30c07988ef8dfc62dac712b9d587daa4a36f2539", "job_title": "UnitedHealth-Group", "place_id": "ChIJIWZRKeHKQIYRXxta3wOMGGc", "address": "1725 Hwy 6, Houston, TX 77077, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.5705632, 29.7714443], "type": "Point"}, "properties": {"photos": [{"width": 3024, "height": 4032, "html_attributions": ["<a href=\"https://maps.google.com/maps/contrib/108143329814504597326/photos\">State from Jake farm</a>"], "photo_reference": "CoQBdwAAAL2JuIj7kCEx71kb4gujh1GFQiXqP9nXJvuoaC5YsPwbrVG6oNLLwiJtnAck1m3DM47sMsM3W-uw_yhf3qInAEhO85OAvRTPxX8agoNOaEPw_lzMrjMfk_laKC4UrfoJ8rlBm7xD0VCJl0d3VuNkqMOshlPYPBsW3uNnBV36HtKKEhB3mgPYFGIjHushz1LkWrjcGhRxTxz1D9Gl8yL7z4QaxqDhTUNeFQ"}], "types": ["park", "point_of_interest", "establishment"], "reference": "CmRSAAAAnxVjggzzxARrkpiw0P4zT31cDTmcLQV-Q7x7SDPBVMu-Yb_kiklmTBSlTnw8lxoXSHPc5v_HF-iiT_d37u2fEEmgSHiw8ngx8LLN9iAoSVdB2Bpn8o4qzvqP0GcIyPYXEhDuoCnQIRiQbBo9SI8FAT6LGhQ9fCRYysZWXMGgvU6AYVaQyzxD-A", "name": "Houston Audubon Society", "rating": 5, "id": "050a5458d86bdd1cee7b09678bd6256d0a20a73e", "job_title": "UnitedHealth-Group", "place_id": "ChIJlQOxwVDbQIYR2uX_TZl0TYc", "address": "440 Wilchester Blvd, Houston, TX 77079, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.56820189999999, 29.770778], "type": "Point"}, "properties": {"photos": [{"width": 1800, "height": 1200, "html_attributions": ["<a href=\"https://maps.google.com/maps/contrib/108765250995932379967/photos\">Audubon Docent Guild</a>"], "photo_reference": "CoQBdwAAAAo8m3jfnpddglp59j6vNL1gSbWYNqy4QSORmn9m-z1dpO05OxxraolrWo7gKL8nYPcvGH3S37vUE_ziwmD8JA1fQpi4ZTNe9tERnT6oUd6-etWoMHmqYqUU7Bc4G6AUB746n6hdrnsW8Hs74998nckUDHaA7Sg_di8ucN0BbFCWEhAJcZZMTR5supoKM0pfdJWmGhSYPTzqpSJkP0eh9fsZ8kIHkPc-QA"}], "types": ["park", "point_of_interest", "establishment"], "reference": "CmRSAAAA7XMSejTP9k7tKq0zGV0ZFXMYHBTQqJsdCGaHr7wgoVJ6ahe7lNb5Y_3xi9grJmrb-iROqH1NCYODkf1HaOtwk6Qdo6q3lkhS7OyDSFkvSDtTZTNrGxc8sw6MEzGs2z8jEhDCfRnYrvxN8EEz8ajrS3jwGhRNrir2osi1P4Lj3fZsEyX9zcljFA", "name": "Audubon Docent Guild", "rating": 5, "id": "7ddd5daf76cc4979e2ba6b062322d1c77d5d1c07", "job_title": "UnitedHealth-Group", "place_id": "ChIJI9XyNFHbQIYRtwHb8EtTpeU", "address": "440 Wilchester Blvd, Houston, TX 77079, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.44932349999999, 29.7803218], "type": "Point"}, "properties": {"photos": [], "types": ["point_of_interest", "establishment"], "reference": "CmRSAAAA2DREgmXD_yUkGH4KGaCwB7-0aZXy-cVV43neLz9xUQG6SNb-qSWVMOkIahMIRU-5EgUNfcjbSC68EV6Bz_kGFFleW9ArO8gGBYO6uZ686NHjhRrnFDeHwssn9tj3jo-TEhBCb4biZVBdFQ8O7aoV4IFPGhR8b9ClRVFZN1GYVaWuyoLhmsznaQ", "name": "Coastal Conservation Association-Tx", "rating": 3, "id": "7258b034e119f31e82320bca6e72781ee9f79d75", "job_title": "Gullett-&-Associates", "place_id": "ChIJcekacM_GQIYRPzL13cgQrPk", "address": "6919 Portwest Dr #100, Houston, TX 77024, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.47039, 29.655454], "type": "Point"}, "properties": {"photos": [{"width": 5312, "height": 2988, "html_attributions": ["<a href=\"https://maps.google.com/maps/contrib/101184977609161362375/photos\">aug4</a>"], "photo_reference": "CoQBdwAAAF-pEfksrEy8s12MB1BjbEw0H897MdW8hW6pPwmdA6tWoSphKP8eUQjKsCmSXppUZ66ILZ2PShlfRJsTIfJzEV8TyWDZE4kFMtlTcKRppQ4pPa0RZzVSTo8iJYu7TIN8YH18Z_qfdwd7wwCGiHldA_BESkvzrF3NpBUzokfsow0GEhBpTo7UzNpCcZgDAcpW7mECGhQiBo0-KzEN45UytNOaSvQGOoEJwg"}], "types": ["park", "point_of_interest", "establishment"], "reference": "CmRRAAAAVSAaDlXOg8bxMzUgJ7sso6RQ1YAv2WMwXjvf6PzBsb3qhuEYtK-JHxyeRrkqp3P0KrGxYzYQVtiSU4Jul768KqRDY6juVTpN0JdflSzWbPF9EwbBe9g3_5ZpQ7izXdMCEhCwwA2d03PanpqERsMTzv0GGhSiymOFXFZzdGEfPvVURvHj6LYYQw", "name": "Willow Waterhole Greenspace", "rating": 4.3, "id": "0127506e8071350c2d48f0ca56e939045297a0f4", "job_title": "Gullett-&-Associates", "place_id": "ChIJR6_2zTzqQIYRsA7wExgfDWs", "address": "S Willow Dr, Houston, TX 77035, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.4003322, 29.7388505], "type": "Point"}, "properties": {"photos": [{"width": 1136, "height": 640, "html_attributions": ["<a href=\"https://maps.google.com/maps/contrib/117056878997299689379/photos\">Marisol Brown</a>"], "photo_reference": "CoQBdwAAAITCzhnbjNOc9nPI4MbfJVGj4G-2RjTGpvtF0LE3_PINGbz4lO-OSR_c5tdtPzv_HBsrDa4huZNJCoyKMjyOLyRnZjSTQDu3xmllZjQgR9SOEE84VtTfG2Jt1fJj9r13jas9CPUv1jhbm72nAClX4EtYHzsL7GLXoMfPWpjMrzJ8EhCt8oGlSB8vebEEdYV6t4UcGhSr43CwoJm6HD6CFHbppJaPOZZzEg"}], "types": ["point_of_interest", "establishment"], "reference": "CmRRAAAA-khATdKpZmJgWOaJlOaE2JeLp_qjkAF_Nz3iEY86Uj8SZUfDZs3tBVl3NH0ZPN0Nk62nVYKxoF70cdJLTdwJZx5jERJH8qcyRnOl-DF0JkHIk3t2vVZqnl2xXVvQ4n1jEhBmzgb-FetX6D6qwrx6QnsDGhTHuy594tDSVx_lbCEu3q7Vi4gXvQ", "name": "Masters Fine Art Conservation", "rating": 5, "id": "a462c2eef4e22ea319485ae7b84f3d20756cbdd1", "job_title": "Gullett-&-Associates", "place_id": "ChIJp8u2bZvAQIYRbosnWz6cVmY", "address": "1612 W Alabama St, Houston, TX 77006, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.3876169, 29.794149], "type": "Point"}, "properties": {"photos": [], "types": ["art_gallery", "point_of_interest", "establishment"], "reference": "CmRRAAAAhYc3kSDGuMHY_UT0rDEKfmFmnuJ5lIuI93pFKFpSFNMqv4Dk6T5svlcai8WxYxI7hwMCiZvuYgFbWrRLjYuhrCPe3Qh1_Tm9N-wGzn1NMyUBv0imm6gCfKdED5jyqAYbEhCwgjjFOe2VGUHQ7hexr6TNGhT6x9jWgzUrftjIeRrO9a7e82mEKg", "name": "Whitten & Proctor Fine Art Conservation", "rating": "NA", "id": "883a8c5ef35ab28e1630235ad65a6b16506a67fa", "job_title": "Gullett-&-Associates", "place_id": "ChIJ8YuXE6K4QIYRn1SF1hazFEw", "address": "1236 Studewood St, Houston, TX 77008, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.3858767, 29.7300997], "type": "Point"}, "properties": {"photos": [], "types": ["point_of_interest", "establishment"], "reference": "CmRSAAAAi9aT6zEfax-KdPJcnEnUBPEbf67yqK28DH3E2ZH8khqeL7KcaPEwRQjSXFO49r6BumuyfCc_5asn1Q-gH0d6FoXJf21xAUdJkvoYNxq36_jWU9K54lKOGVHS6cV2oWZsEhDBtAoXxUpN3_HSydmSNuU0GhSk-YJr5pyoAmlz0FmntcHOYpJnkQ", "name": "St Mark Fine Arts Conservation", "rating": 5, "id": "ea2d4bac6d74716b33f456dff3aae0cc0b43cca3", "job_title": "Gullett-&-Associates", "place_id": "ChIJKbDEoXm_QIYRcRFBlp0dE8A", "address": "4901 Main St, Houston, TX 77002, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.483218, 29.7482286], "type": "Point"}, "properties": {"photos": [], "types": ["point_of_interest", "establishment"], "reference": "CmRRAAAAuhbozA9wxp3_lDa7zs58v1uBTfhCpH00pOxiHbzz0DoFzBC0bQ8JmWPO0nYAPclMWJz8djzBdYaWXljSA1qkzNS7UnCeG5_7XKnOITsjnXmUvgNIslXCMyWoHhyceW5BEhBzn1JyTqA9DqAoau_AZC3vGhTY9-mC01_zR9uXitUbIAWat3blyw", "name": "The Nature Conservancy", "rating": "NA", "id": "90af6fb9fb926dde9f7103577cebc4150bbb1dec", "job_title": "Gullett-&-Associates", "place_id": "ChIJq-m4EX3AQIYRJkn4Lhccp2E", "address": "1800 Augusta Dr #240, Houston, TX 77057, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.42318089999999, 29.7345943], "type": "Point"}, "properties": {"photos": [{"width": 750, "height": 437, "html_attributions": ["<a href=\"https://maps.google.com/maps/contrib/106788706324997826205/photos\">Erika</a>"], "photo_reference": "CoQBdwAAABO2w9STDOxTK39SngA53Vr7lvjRwPDKzTA5Q0woP4PzyNrZQJ-1jA2slPetL5PTy-DzSLZTUoSVmsRSZC_-OKEU86UjiTNMAUMtbTFe0e-I_50s3Nf_Hh-vm0j2_rQbB-ip2ooWr9x9WED1xmoJZtbLOQLNYZCTU9_5oGfhdcqFEhCJnzNqo6XN0pJPJTyxJjoqGhQCvfgwkbTlY8ikPk5a5TlHB6GrtQ"}], "types": ["point_of_interest", "establishment"], "reference": "CmRRAAAAyQe_KElunoAY5_BG2j4BSpl7L975-gA8z2gLuwBUgDJtUajrP-kenopBVfG38XH7ds8EbGdbWljnuzFZlSjaWV3-kpiSl0L_dWvcOiPxZ6LFP-wJ0EEGWg9GWv7TPy_QEhD578E9tNPni5WzzfuVtT8QGhRdV1G5VGsIZ3zkHV0C7U-ymjWjmw", "name": "Student Conservation Association", "rating": "NA", "id": "1c5ea7722fc0d99e9f7dfca55f5d9078224d51d3", "job_title": "Gullett-&-Associates", "place_id": "ChIJQcqBXfDAQIYRErawO-goGj4", "address": "2990 Richmond Ave Suite #400, Houston, TX 77098, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-96.038102, 30.055621], "type": "Point"}, "properties": {"photos": [{"width": 984, "height": 985, "html_attributions": ["<a href=\"https://maps.google.com/maps/contrib/110279808588468038448/photos\">Peckerwood Garden Conservation Foundation</a>"], "photo_reference": "CoQBdwAAAEprKM4bXo2sSDPlY53NIOzctcBnRYQnToRXJUgo3xvzMYsquK8n54E9PsPjqzDL7vIMvlqReUScACOwVUv_wesmAAvz_ubvrwlRdK5dOgrFFvsmzI0Xa-b5J8VTDmgrpvGPXk1nNDFCEcmvMe7JS95cIgXcN9rex7uAzRS94VePEhACryTVc4ZbWvMqWcjIcbDuGhTzUQVTrXQ0xiN94cuBhNd-y8VO_g"}], "types": ["park", "point_of_interest", "establishment"], "reference": "CmRRAAAA1g1QtgRA7Fspfn0adOJQ7eVLVqr9K5VYcbrF2TFtvMYVsOh0PS35mn9JUUxOU0_wto2T9_ifEF-ZshjtzJyTBzMkJIU28vj4ebUAIH9Y-w5fvuw4cjhQNoFQ7VFojXgVEhDIS5ckYnx2OJenUh3JC4RfGhRVBQYCsuMACuM8Q3TJ1NXScufxFw", "name": "Peckerwood Garden Conservation Foundation", "rating": "NA", "id": "e618a4c618cd67ce4f5fdc165f640220ab3b53b2", "job_title": "Gullett-&-Associates", "place_id": "ChIJmUR7pvHKRoYRIIl0o73bPGE", "address": "20559 Fm 359 Rd, Pine Island, TX 77445, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.64386449999999, 29.7515036], "type": "Point"}, "properties": {"photos": [], "types": ["point_of_interest", "establishment"], "reference": "CmRRAAAAAd6La0Vb_4j5fzMocDIHh02Bi7t0iTUHg0HReBvwd76Md6OEm0JOCRrAdThKf6419DZFwYAwcWnLiU1ZJXxvZt5d4NI7rQYDjkAwshsQ-7__v2tGpe11RWUb2opIe09-EhBOSDVBGG8gRKmvHYePvsMzGhRBTgaQHI5ZNzXfXyS1-v9sopgpnQ", "name": "H2O Conservation Technology", "rating": "NA", "id": "30c07988ef8dfc62dac712b9d587daa4a36f2539", "job_title": "Gullett-&-Associates", "place_id": "ChIJIWZRKeHKQIYRXxta3wOMGGc", "address": "1725 Hwy 6, Houston, TX 77077, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.5705632, 29.7714443], "type": "Point"}, "properties": {"photos": [{"width": 3024, "height": 4032, "html_attributions": ["<a href=\"https://maps.google.com/maps/contrib/108143329814504597326/photos\">State from Jake farm</a>"], "photo_reference": "CoQBdwAAAIaJXzi5G0EF6FNO22EjJYhlTo1egTtTwnOZPkDG9r4bTTS6ysbssVQBVa2_es5lSfD7giWIz45DhfbpndR0D7zHqlpqvM15vaFj1UzMlD_cTZpjDnTTBQE24wICYRIm38tgEDetw9DrAzydS0VZMeF3GJ0vzPrQkYQvKem1eLjCEhC3lmIbhTQipAdYOH7B4djEGhQQnZ-REzAaJqcOoZhU6RrePORt2A"}], "types": ["park", "point_of_interest", "establishment"], "reference": "CmRSAAAASzZPp6CCdkbGddR2QTWzRrCnjz6nxmVrfiyiymit8fhKMJjlT_ImHoCTnk2aFMOJImzL_KuVGRul4cW8dyH39YuJFLFUV7C5lz6Y4kOpEpvpqIUUTTmnou40R4lockXWEhAlaOAKAwqN8dDQN7pNWR3vGhRthWL3zn29FvDE0i42dH02C3Ccng", "name": "Houston Audubon Society", "rating": 5, "id": "050a5458d86bdd1cee7b09678bd6256d0a20a73e", "job_title": "Gullett-&-Associates", "place_id": "ChIJlQOxwVDbQIYR2uX_TZl0TYc", "address": "440 Wilchester Blvd, Houston, TX 77079, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.56820189999999, 29.770778], "type": "Point"}, "properties": {"photos": [{"width": 1800, "height": 1200, "html_attributions": ["<a href=\"https://maps.google.com/maps/contrib/108765250995932379967/photos\">Audubon Docent Guild</a>"], "photo_reference": "CoQBdwAAAEriEBKzYlbnQELcArqkhmAjVTN8pjFkKvOqP_RJLBRmfPEGetHRXpiwkhZOZZj5bX4-Cwr8wVy0hReDvBUd5vD5sel7LaC5neejx1LdQQQdrohUR_icozWFmjrUB4aCBAtbZ51FAnYzcckAohIMI-Lz_ceQb8jLURLpI9Q6_eIGEhCEMHQNqggQhFGwt87-P7WGGhQWtzWD7Yy_f288FO7so6_O8RHhzA"}], "types": ["park", "point_of_interest", "establishment"], "reference": "CmRSAAAALW0SB8PL2gLjzQe75mOSzWxQSeSQ0WXp5arpFgA0SvaYcZT0NPaVYdAtYIs0CfiB9H-XA8IPpdl6ZFPzn_VVvSfJG9ug3mMpaq9EbrBm5-261nb__O2sgA5vlLynOoUvEhBeTJGCkQTRHwdongG-MV__GhSysxShQvqWt9AiqJySwtE2p-CbQw", "name": "Audubon Docent Guild", "rating": 5, "id": "7ddd5daf76cc4979e2ba6b062322d1c77d5d1c07", "job_title": "Gullett-&-Associates", "place_id": "ChIJI9XyNFHbQIYRtwHb8EtTpeU", "address": "440 Wilchester Blvd, Houston, TX 77079, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.44932349999999, 29.7803218], "type": "Point"}, "properties": {"photos": [], "types": ["point_of_interest", "establishment"], "reference": "CmRSAAAA0uXQqr_IO5s7bRwPQTmeg8x9LvdfaposDM95n8c5xL2ZfeNUqAO9h23B71L408_pcJa7KXvxQX8-pJCboDmxgK_p-gqrLDVkwnThKl8ZIqGXr5f1RbZhFyv521V0E7P5EhCcX8NNE4epFspPxxzEmfNkGhQ3rvxSlek0uMXyyVDY85OQ5U72Sw", "name": "Coastal Conservation Association-Tx", "rating": 3, "id": "7258b034e119f31e82320bca6e72781ee9f79d75", "job_title": "Liberty-Mutual", "place_id": "ChIJcekacM_GQIYRPzL13cgQrPk", "address": "6919 Portwest Dr #100, Houston, TX 77024, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.47039, 29.655454], "type": "Point"}, "properties": {"photos": [{"width": 5312, "height": 2988, "html_attributions": ["<a href=\"https://maps.google.com/maps/contrib/101184977609161362375/photos\">aug4</a>"], "photo_reference": "CoQBdwAAAKk6s6KAaSQWGhu0AGAgJUrCWvbmZ8hjWY2TqZL7Ev_aOl5WkXYSIsIesvxQRN-bHaav2OWFbkZTl2lHKJ7-z6T0YZ6tl-mSQMkfxKjVZETVtZoWoxM1QWW4NfTtMGhWBrwFjjoopYgCdXeNL-g4-1nYUGOGDsGLQTKSfOPO2F0mEhCE1K4D2vw-TqLw_rmjXTe3GhQEuuweYeRDWHSjLKC3vTXJVcoxYg"}], "types": ["park", "point_of_interest", "establishment"], "reference": "CmRRAAAAspxoIatu7GU0xutE9-f3HioiclDNI0JQTQ-cNjQhoSkKPOZ1gS_muhEbm5RFtBmn6VX_wyKyvq6Zqn6plZhkkZysTfrUr4JkK71m-QA4DG6ihzsKIWOESdhvK5jBhQOEEhCYd-btFQVd_xSrhxrrAt1EGhTf4egEnxJhjpncli14YLQH_uajyQ", "name": "Willow Waterhole Greenspace", "rating": 4.3, "id": "0127506e8071350c2d48f0ca56e939045297a0f4", "job_title": "Liberty-Mutual", "place_id": "ChIJR6_2zTzqQIYRsA7wExgfDWs", "address": "S Willow Dr, Houston, TX 77035, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.4003322, 29.7388505], "type": "Point"}, "properties": {"photos": [{"width": 1136, "height": 640, "html_attributions": ["<a href=\"https://maps.google.com/maps/contrib/117056878997299689379/photos\">Marisol Brown</a>"], "photo_reference": "CoQBdwAAAIUL_hYXNWiBG0c-KMCDG175RNrLIRztzuFqJEb9aS89RpmUHisXZQUl-zufRD6LzaB_GaVSynxZTVRtoL2MnvC9rvIdXA2Q0mDiCAWf_crsaxIxG_LVbIKKmRauFFY-k9xbM4eUn1X-zuioOjpHuOJGy8ZG40GZmlnj5CI42nIhEhA-JfgU8wbtiKhRLPSmQXYDGhQxgOxxPsk3Bb9HEgnWGZbJ1vmXFA"}], "types": ["point_of_interest", "establishment"], "reference": "CmRRAAAAXc3IcCmNobBqwtEiKaf7bP-3d1UcmOdGvfdWW9FPzKV_R2RaQHy0jQkHp9REWQ10Fw33xoIr8e0ttDCcOSUG7NAMRF32IrzmC1abS14erSOX3Xz2RB8gu0Wxy3spESObEhBoGQjxyNFOp-SOKCvs5t6hGhQWwEGJQewbqrxzJ-HwR2PlkiNlPw", "name": "Masters Fine Art Conservation", "rating": 5, "id": "a462c2eef4e22ea319485ae7b84f3d20756cbdd1", "job_title": "Liberty-Mutual", "place_id": "ChIJp8u2bZvAQIYRbosnWz6cVmY", "address": "1612 W Alabama St, Houston, TX 77006, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.3876169, 29.794149], "type": "Point"}, "properties": {"photos": [], "types": ["art_gallery", "point_of_interest", "establishment"], "reference": "CmRRAAAAhiF-OKrUZyzQKazZ-Vi3s-bQTwZUpMXqbJC7LdbCorfzJ1B_m5I1bR1T_WaqdFhctP4AhFiTIpvDAe3Di-MjcA4GCsSB9FsRYl1nt850FT7YBrbRyCfzS6jqGVEbiBMhEhDMEoV9a0yAoHoD5DHx5V9IGhTdAQWzU3OX429SlgBOZz29RGoB2w", "name": "Whitten & Proctor Fine Art Conservation", "rating": "NA", "id": "883a8c5ef35ab28e1630235ad65a6b16506a67fa", "job_title": "Liberty-Mutual", "place_id": "ChIJ8YuXE6K4QIYRn1SF1hazFEw", "address": "1236 Studewood St, Houston, TX 77008, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.3858767, 29.7300997], "type": "Point"}, "properties": {"photos": [], "types": ["point_of_interest", "establishment"], "reference": "CmRSAAAAQCFwZiwYXwD-eDEccFlw_6BczKTJnCKLT1CIFz-gfbhdYSD7JGkE8UUWHRBdQBBE-kFFpZqP-UjY-F66Z6fJo2E5xDqGwWQ5vV5BykcdMBgIgLlJe3Rnosmnx3EN3P2GEhB7YB2St5b20G0436IVmcMJGhSRt3waQPLdguIelODpToqOi7xiUQ", "name": "St Mark Fine Arts Conservation", "rating": 5, "id": "ea2d4bac6d74716b33f456dff3aae0cc0b43cca3", "job_title": "Liberty-Mutual", "place_id": "ChIJKbDEoXm_QIYRcRFBlp0dE8A", "address": "4901 Main St, Houston, TX 77002, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.483218, 29.7482286], "type": "Point"}, "properties": {"photos": [], "types": ["point_of_interest", "establishment"], "reference": "CmRRAAAA4hkYjPP9vQpPOlMSL6crnKKrRo6u1-LyutDYMPNxrbVVbhFbzt1fHaxeCfxQbhfY7saKvn5kkcFP8KFDcVf3CaiK-VklNEHtSdAa5Ow3OSGAjE7RDpxIBtNFOuosKDVaEhCRbHaP2MTUZd-VV1fb0xU1GhTPlgvncGpQ34tlhDZkWP75DehjXg", "name": "The Nature Conservancy", "rating": "NA", "id": "90af6fb9fb926dde9f7103577cebc4150bbb1dec", "job_title": "Liberty-Mutual", "place_id": "ChIJq-m4EX3AQIYRJkn4Lhccp2E", "address": "1800 Augusta Dr #240, Houston, TX 77057, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.42318089999999, 29.7345943], "type": "Point"}, "properties": {"photos": [{"width": 750, "height": 437, "html_attributions": ["<a href=\"https://maps.google.com/maps/contrib/106788706324997826205/photos\">Erika</a>"], "photo_reference": "CoQBdwAAAPiis3ppnSYm5HTrHYQFlxOJZdJFzhz6QdB27-asqzuiFn5PyfZ3R_PCyMOh8nVYmjQ3R5Y01tNXgoQ8xyh4yL_6ZOEvfPOd0EmhE9PXcrheJhvuapL1bbxvzC8zFoF7rL5V3A4tYRsyocu8csQasxo8vX_P61jJhrQfBhpLTn7zEhCzPUW4VxEp3VbHjXDdrE_wGhR9AtQajFF0i7sVzi7GbWavvjbwBg"}], "types": ["point_of_interest", "establishment"], "reference": "CmRRAAAAQVCtxDtO8VVq8Hy99vl7RIXgYj8m6wKnOp0XR9iNoanLn5dlzI_3xqtDNbZFnPTbtc1GUBv0ibftfhW2c8-RYm00OROQb7aOngYpLBvaU4-p_AqjMThCPuMezK36NmRYEhDW930gcr-JIPLSesRq4_z6GhQq8-Le75rp3nhaagXE9hMeUNqkEw", "name": "Student Conservation Association", "rating": "NA", "id": "1c5ea7722fc0d99e9f7dfca55f5d9078224d51d3", "job_title": "Liberty-Mutual", "place_id": "ChIJQcqBXfDAQIYRErawO-goGj4", "address": "2990 Richmond Ave Suite #400, Houston, TX 77098, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-96.038102, 30.055621], "type": "Point"}, "properties": {"photos": [{"width": 984, "height": 985, "html_attributions": ["<a href=\"https://maps.google.com/maps/contrib/110279808588468038448/photos\">Peckerwood Garden Conservation Foundation</a>"], "photo_reference": "CoQBdwAAAMizZdt_GYTInj_TS9axparp171I_RO95QAGmULiyTdetbiw0RGep0p6_Z55De_RD1uJBTHfW3sToOh2H7zP6j4fx4gI7I2PjNLsyIQxPEhQJiY6uYM8jgKXI9YDTOcqBiiTfneBa3RGeKwENOKPDpRVHpVHaAXkUODJ5KAPJk3lEhB8PeoOPW7O7CVXyLeaHN49GhRQKgcS_3g2pOKPiz5Plg-AWSo_6g"}], "types": ["park", "point_of_interest", "establishment"], "reference": "CmRRAAAAUnHvGhWdcUGehB8tbgXC5frHlQErLE0bdAEomLsYtp46CCHCwwLqtFkJkM6NlXXAbACTVtnvBOLb0MKME36RflCOuXmgEFa4ym-NwI3QAbdaw1_rr26XpGZCNenubIb_EhD2IbLCaH54bcLrIHaaFrvkGhT6CcCxZlnz0wcLnsOFnvLNCOyuPg", "name": "Peckerwood Garden Conservation Foundation", "rating": "NA", "id": "e618a4c618cd67ce4f5fdc165f640220ab3b53b2", "job_title": "Liberty-Mutual", "place_id": "ChIJmUR7pvHKRoYRIIl0o73bPGE", "address": "20559 Fm 359 Rd, Pine Island, TX 77445, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.64386449999999, 29.7515036], "type": "Point"}, "properties": {"photos": [], "types": ["point_of_interest", "establishment"], "reference": "CmRRAAAAGxzc_Ol7Sg98na0iPEnJkjhNKsUq0W9YQBSBlPWRlr_lXC6jXg4_RvSo7eMyIbCHqqBoctiC9YwUuaqmIrl0fNxBK2pKiQE2cEuVvvjQmRmzDBefRIQ0ZJQSN-9WWIhZEhCb5DnFxQsdGAC4927i8UtvGhQlhCA7X8bzkgdGYY8JuB0eA3JbNA", "name": "H2O Conservation Technology", "rating": "NA", "id": "30c07988ef8dfc62dac712b9d587daa4a36f2539", "job_title": "Liberty-Mutual", "place_id": "ChIJIWZRKeHKQIYRXxta3wOMGGc", "address": "1725 Hwy 6, Houston, TX 77077, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.5705632, 29.7714443], "type": "Point"}, "properties": {"photos": [{"width": 3024, "height": 4032, "html_attributions": ["<a href=\"https://maps.google.com/maps/contrib/108143329814504597326/photos\">State from Jake farm</a>"], "photo_reference": "CoQBdwAAAJeGlKRGi76T1ZXyDfoBxa7Lw6Dqag_FachjX56H7pe1Enj4U07yI55JjBwkD0eT-Jk3xvRvjs4ZtoBdgaejnaqSKUCPKqADpb_T7BJKN27gPTHN0W-UwizwQGmH5_zIzfGRsW5D_8B0O1awQymGtETPnsjArchGtKcnJLf1b1NgEhC6_WZhZt-3Sizzq9roO1K6GhR-gnbnoA8Ioeoqk5SFubDvCNbi9g"}], "types": ["park", "point_of_interest", "establishment"], "reference": "CmRSAAAAQuAOpHOKh-iItVKApN7tvRxJNU6N11plSkmHc2ZBNhgISn_LFbxcFhPekvb5ySQWgEyHaMcNC-y5O0OWcgpMhnLthTtuaYPbQfKMlxiJWh7vOEykjadSJi6jbbcra_AMEhDFYL-mf7g_jY_JLKZiusi5GhRiHmYQaEZxEYJbITW1oP0I4BmdMA", "name": "Houston Audubon Society", "rating": 5, "id": "050a5458d86bdd1cee7b09678bd6256d0a20a73e", "job_title": "Liberty-Mutual", "place_id": "ChIJlQOxwVDbQIYR2uX_TZl0TYc", "address": "440 Wilchester Blvd, Houston, TX 77079, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.56820189999999, 29.770778], "type": "Point"}, "properties": {"photos": [{"width": 1800, "height": 1200, "html_attributions": ["<a href=\"https://maps.google.com/maps/contrib/108765250995932379967/photos\">Audubon Docent Guild</a>"], "photo_reference": "CoQBdwAAAMElQBvou6Eo80ALlPe52W2WtTUV3nWknOBFVeWXyEjR5pc94O0iuU8HCpPkHZMw0DeAjfkUlEIU6IPJrO9xalt-u_6w9OZfUHkwSBi_JRU4Hlj3snAkd1W1_5Htfo1Q4bISUdxM4QctxHHLYEW6EjV8ZQVuIXWesDs2tZP0vn2nEhAF81PlrVx_uZsycAFObABlGhQBknIPVuN8R-AWpNRYdcgrL7eIWQ"}], "types": ["park", "point_of_interest", "establishment"], "reference": "CmRSAAAAsSR12r7uhNfSi5jD5stP6pJ80rSZeGLaGpwXke1b3nllZZcOy309NbP3aK6zLh6uyIx-KfpElZ5BYkb2nMSRny0gr0clOqPhHlnW4RciwCtBP3L9gOeMUAktQ_LNb02IEhBFFvTGZXhBG37f36SA8E6lGhSlPjWbuUZVMJIA48tYCnPpIqKzNw", "name": "Audubon Docent Guild", "rating": 5, "id": "7ddd5daf76cc4979e2ba6b062322d1c77d5d1c07", "job_title": "Liberty-Mutual", "place_id": "ChIJI9XyNFHbQIYRtwHb8EtTpeU", "address": "440 Wilchester Blvd, Houston, TX 77079, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.44932349999999, 29.7803218], "type": "Point"}, "properties": {"photos": [], "types": ["point_of_interest", "establishment"], "reference": "CmRSAAAAh841TN_xhKkamnCSaG7Pz5oMghhsQeB74ol371MX8DkLu9qWb7PZPkErkHDFBtArZOqxCtY2KNK9uIpEf3m3CShHlczY5RmLEf3WRa9J0tLChVOL-qX64y3Xls-sZOGGEhAuQft6oUTWahqbRBmR3wBBGhQWuRWJrZwdkbQ9L33waRYY7BOhxQ", "name": "Coastal Conservation Association-Tx", "rating": 3, "id": "7258b034e119f31e82320bca6e72781ee9f79d75", "job_title": "Gane-Technology,-Inc.", "place_id": "ChIJcekacM_GQIYRPzL13cgQrPk", "address": "6919 Portwest Dr #100, Houston, TX 77024, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.47039, 29.655454], "type": "Point"}, "properties": {"photos": [{"width": 5312, "height": 2988, "html_attributions": ["<a href=\"https://maps.google.com/maps/contrib/101184977609161362375/photos\">aug4</a>"], "photo_reference": "CoQBdwAAAJNa-_Q4beywnzUry0GA-eo7NtRT8eff_yIy1rxlPkxldm_qXwcnYtq-rUgta3yfJIxS9zE0ySlMNQ5fY1k5WsWY3iNaAIReU-bnaixM42Vx93mRTfdGgMNfE0gPmdJeeFneIaF-0LmW3YbhM6A2yxVbpQl0s0IBjnJOabGRR5H3EhBnGSut8QdnKvZZ5fcCMHHQGhTO-M3yrQsCUoL9k9_jI95DzAsDsQ"}], "types": ["park", "point_of_interest", "establishment"], "reference": "CmRRAAAAC9Pv-D5vSLTGm-obcfGxR-Slbkj10t7VmYRTqbAXiTNeQ9dgjnS5cWrH4RIfw18910FiHSGMTn6LvzFARpKpvPf48hNEwO180OrymIg1Gk1VP3fniIBFCs-W5c1gHqhAEhC8tnjAsS9TwmjLntTqjUYsGhRsaIIXI_cdYRruegXhMeTPWEhvGQ", "name": "Willow Waterhole Greenspace", "rating": 4.3, "id": "0127506e8071350c2d48f0ca56e939045297a0f4", "job_title": "Gane-Technology,-Inc.", "place_id": "ChIJR6_2zTzqQIYRsA7wExgfDWs", "address": "S Willow Dr, Houston, TX 77035, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.4003322, 29.7388505], "type": "Point"}, "properties": {"photos": [{"width": 1136, "height": 640, "html_attributions": ["<a href=\"https://maps.google.com/maps/contrib/117056878997299689379/photos\">Marisol Brown</a>"], "photo_reference": "CoQBdwAAAN0sOmSCDENcP1xWzrzizDwSMJbocN4J05vZsL-iFv49xOKIn7Ok0m-tMZvTghc3RAI1ZpoAqLDgC54px3ugX4hvix2RinZh0RWxRJRm8IQw17UW0KQAYubGNes74hx846RHsSaqU_jMS8RBCafzxzkgLxwsSBZm4iLS_5Cm8BdlEhAJmNcGHLGNOSM1HJOfZ61LGhQe8a-e2imdAn7aShEMRUu5Sxgl_w"}], "types": ["point_of_interest", "establishment"], "reference": "CmRRAAAADel6-GUXB1Ft-dImy3Ngq4H1uYS2mZqtZqU4laJQWPt2tCnf6NziA_WmExadANF7nO3M-ql6x11VqTyBixDc9aAMyqYqHvESfn8kl-JZZVUm3C55ab-wbKb_EbbB7KchEhDM14mtmkQx1rxyEdfH5x_OGhTDTWVxrvYwXcbPnRifsX9I3diECw", "name": "Masters Fine Art Conservation", "rating": 5, "id": "a462c2eef4e22ea319485ae7b84f3d20756cbdd1", "job_title": "Gane-Technology,-Inc.", "place_id": "ChIJp8u2bZvAQIYRbosnWz6cVmY", "address": "1612 W Alabama St, Houston, TX 77006, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.3876169, 29.794149], "type": "Point"}, "properties": {"photos": [], "types": ["art_gallery", "point_of_interest", "establishment"], "reference": "CmRRAAAAUv8Mx7NqqsxXqhqjFE8InzdxAVWXGHcN03gP9el-9gScEr8e6jArnEZ-6_G12_y22QtJ4lLGOqfBAcYinIWehtHiRtUxJOl7KRr8o00i9wKwF5NXNOctQGE1oQymotXYEhC1QywDifLjR_JeZ-UDdUPUGhRdpCmHgeVEul4njoDEgNzw7lcNTQ", "name": "Whitten & Proctor Fine Art Conservation", "rating": "NA", "id": "883a8c5ef35ab28e1630235ad65a6b16506a67fa", "job_title": "Gane-Technology,-Inc.", "place_id": "ChIJ8YuXE6K4QIYRn1SF1hazFEw", "address": "1236 Studewood St, Houston, TX 77008, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.3858767, 29.7300997], "type": "Point"}, "properties": {"photos": [], "types": ["point_of_interest", "establishment"], "reference": "CmRSAAAAzqoddUCCOlR0z4qedCLSdX6F2MFMABruKbvH14hfMVVeFV8tyHZvzUFXLPMuRv17Y0UjXCU4CgqlhXTPVGwZmqHQ4oQtrUmaZGRMF1vCVb5duN440Pzjmg5YbMdi-D_GEhC3ZPMZyuuhiy5vCb_5W0AGGhQXkA4H6EihEnREuiljIFH9ve5xCg", "name": "St Mark Fine Arts Conservation", "rating": 5, "id": "ea2d4bac6d74716b33f456dff3aae0cc0b43cca3", "job_title": "Gane-Technology,-Inc.", "place_id": "ChIJKbDEoXm_QIYRcRFBlp0dE8A", "address": "4901 Main St, Houston, TX 77002, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.483218, 29.7482286], "type": "Point"}, "properties": {"photos": [], "types": ["point_of_interest", "establishment"], "reference": "CmRRAAAAlIahPkUiyOtdBLFxUps-0NU5nWXTJFrR_9zBRDhdyBtxkhI2I5v0W9d8OewAbvLcvTH-ckqGz2cl3DPgqFypSimJTINQtylTX6yfLu4lW9WylgFHKItjyQoTdvRrGRywEhCcqOcON541PSE1zAKQqidhGhTFkJGD7iuE89BG3hyfUJUFa3n_3A", "name": "The Nature Conservancy", "rating": "NA", "id": "90af6fb9fb926dde9f7103577cebc4150bbb1dec", "job_title": "Gane-Technology,-Inc.", "place_id": "ChIJq-m4EX3AQIYRJkn4Lhccp2E", "address": "1800 Augusta Dr #240, Houston, TX 77057, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.42318089999999, 29.7345943], "type": "Point"}, "properties": {"photos": [{"width": 750, "height": 437, "html_attributions": ["<a href=\"https://maps.google.com/maps/contrib/106788706324997826205/photos\">Erika</a>"], "photo_reference": "CoQBdwAAAAj5n3rgV0iB_k3Q4WRXhtbQig31x0p7RyF19yBBI1RwXEh64_v075pZk34M6ocl_A4wGFZmSU1UZip0wMyZSR9PJ63geFb1SRgW_UEfOkwFO5CitDQwjnMacY_4CJmuPSnenLqgD6UlZtZNQHnijGQq1IO2as4u7HzxZ0lcq-DSEhDvXzF_ZegOuMjcHmt7jQtBGhTU7oLHGICewoxFbz8WzdtgKLmWdA"}], "types": ["point_of_interest", "establishment"], "reference": "CmRRAAAAjI8LGF9lAAqK_OUHts0Lwwq_Z8BsniQdXWucIYaKuWlei9SJ7t1pMnIvHJvAWTKlWJjajqbP84jAo9x-aE15Q5dcgExcts4V1a2ZBjENXV72f3zC16gIrus5XK_kfoNxEhDPNKVSp2Gdgvy0pBmgFiQxGhTsElr1SXmLtPNslbtVIF0cEF5pLw", "name": "Student Conservation Association", "rating": "NA", "id": "1c5ea7722fc0d99e9f7dfca55f5d9078224d51d3", "job_title": "Gane-Technology,-Inc.", "place_id": "ChIJQcqBXfDAQIYRErawO-goGj4", "address": "2990 Richmond Ave Suite #400, Houston, TX 77098, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-96.038102, 30.055621], "type": "Point"}, "properties": {"photos": [{"width": 984, "height": 985, "html_attributions": ["<a href=\"https://maps.google.com/maps/contrib/110279808588468038448/photos\">Peckerwood Garden Conservation Foundation</a>"], "photo_reference": "CoQBdwAAADCq6JfvJUxYLnlRzHoUVXU3BhoCwSzuMETYCqaZrLS8gyw7IDSGtn9JCU-MF5cBj1lDQ-5F09NPm_UBQzHST9Fl38E3zZFHPtKusNtGL2-XAly3xxDMF3DPBsPw_vokZhMFkyR5cYhBDDjIyXRaaRl96mkANMy2cOh1_H8BcdGtEhAHR42jOuWVvGZwzA966bbLGhSCqH8LXeRs_-kg0l5sABMYRDXMLw"}], "types": ["park", "point_of_interest", "establishment"], "reference": "CmRRAAAApA8KKpGWRdzkvjYBrltpKD4JgNsDC4b61Qxjdurm1dvbZ0xuk_WjKTAKyJNd5KvZTMqsVFTO3GjBj9HDoNQqOCaeol7Z3KuHo4AUv0cQ_o_DOCPIbTMqYw5Jmi2PLQ3uEhAqZSqXq2gRvx9MCx47IpLCGhRQmZ5lANzhnwv8d4CESMtqqDlceA", "name": "Peckerwood Garden Conservation Foundation", "rating": "NA", "id": "e618a4c618cd67ce4f5fdc165f640220ab3b53b2", "job_title": "Gane-Technology,-Inc.", "place_id": "ChIJmUR7pvHKRoYRIIl0o73bPGE", "address": "20559 Fm 359 Rd, Pine Island, TX 77445, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.64386449999999, 29.7515036], "type": "Point"}, "properties": {"photos": [], "types": ["point_of_interest", "establishment"], "reference": "CmRRAAAAuyV0wCIY5nnpcuIKj5EQxabTdJMmjw-p4KbEzW3JwWu144czk1WW5cMG9RkLph-HNl9xhA2IsB1nMLz2AjCc3ZkKMtSzftQE0zNI-sIh27Vdf2vKnm64Gz14PjzsGaMFEhBeOjydFa3aVpWu0uiszSLaGhTMA_aZmfX-MIsJ0BZ6XVvW5gilQg", "name": "H2O Conservation Technology", "rating": "NA", "id": "30c07988ef8dfc62dac712b9d587daa4a36f2539", "job_title": "Gane-Technology,-Inc.", "place_id": "ChIJIWZRKeHKQIYRXxta3wOMGGc", "address": "1725 Hwy 6, Houston, TX 77077, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.5705632, 29.7714443], "type": "Point"}, "properties": {"photos": [{"width": 3024, "height": 4032, "html_attributions": ["<a href=\"https://maps.google.com/maps/contrib/108143329814504597326/photos\">State from Jake farm</a>"], "photo_reference": "CoQBdwAAAL0zwM46ngMHgVZgmzK1Ugfgf-MH_3xl495Qn76RlkKXWwVSo6EJXfGHcjfcKs3cCSf841eQ8GvXeiEEYhtjnmZE-jXhf_7IYwNNSDvg10TUKiqtqRoBxjjVD2q-zUGDqCuW1hVomRpMdhWkppz357eKIW5pwjldulkEfMgnyqsuEhAFwnxUMzCVacy7D-NdnnPWGhRrlcoZys20e8gmpltWiZFRihljVg"}], "types": ["park", "point_of_interest", "establishment"], "reference": "CmRSAAAA5322MMNg8nEtf7qva8LAsLjNRvAHSmAx4IBtOwwTo1SizC791ROUO8Q1cg1yMZNJbhMSZF7ixsh7K2DtLkPXkVq1DhRW_QQVO1-QpU8UJtF_owQNrQSm6uuqxCHNhzb8EhAmQCH0JVjxL0WdJaN00JbOGhQS-r2PvRhd4ehFqKUtgTSMthcjYQ", "name": "Houston Audubon Society", "rating": 5, "id": "050a5458d86bdd1cee7b09678bd6256d0a20a73e", "job_title": "Gane-Technology,-Inc.", "place_id": "ChIJlQOxwVDbQIYR2uX_TZl0TYc", "address": "440 Wilchester Blvd, Houston, TX 77079, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.56820189999999, 29.770778], "type": "Point"}, "properties": {"photos": [{"width": 1800, "height": 1200, "html_attributions": ["<a href=\"https://maps.google.com/maps/contrib/108765250995932379967/photos\">Audubon Docent Guild</a>"], "photo_reference": "CoQBdwAAAJXj0_w29MSw6Cxp5NocacK3p0IB9wlxrDwF760qmTHzKpaMxMxaBM1y-gDJCrd7F4SK6O5OUYx29PNXP9cr_Xy61o3wpBtahOutWwTHt_thNESWr-TkpGE8UKW5r9zbPEz6uToOrHaFbEnlMhtzba6jmak8bTz_tbJP23ZyNqdPEhATrWScdFRqu_R5wHq4NxMGGhTGS9N0_KbqrqBy0jnUovroHcfVVA"}], "types": ["park", "point_of_interest", "establishment"], "reference": "CmRSAAAAWr6vmtXu0vFaiecAsjlx3pCwW7Izwm-9RB0nrTgoMV6E5lD_hIFhQzoRhso4sByfsCFZ2Xk-YWwqxnZQAQ2Z0kco33wWnu8JoxdbazZyVHOnDFBO5bBlvXQziLJGyj_QEhD5K2H82XgpqpJgbDTiaCFgGhQ2kikT3CoDpwBHuPiPM9Zuu6Vvpw", "name": "Audubon Docent Guild", "rating": 5, "id": "7ddd5daf76cc4979e2ba6b062322d1c77d5d1c07", "job_title": "Gane-Technology,-Inc.", "place_id": "ChIJI9XyNFHbQIYRtwHb8EtTpeU", "address": "440 Wilchester Blvd, Houston, TX 77079, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.44932349999999, 29.7803218], "type": "Point"}, "properties": {"photos": [], "types": ["point_of_interest", "establishment"], "reference": "CmRSAAAACo_5KuwBEZ0d8ym7em7i2UN53R9Ywaelxdb2CUTBOSM5i9Y60WI36vFihyCDpmCpBIcdjNqjyq0dJx3opVYgelPzEt_trk6FgG3JoJeqN_b8DD202fi04WQt_nnoqmHmEhCx9Qkt6gDb-oHUNEwGVFCUGhRWkBxih13tgJ8RsK1JqM0JZ5Uo6w", "name": "Coastal Conservation Association-Tx", "rating": 3, "id": "7258b034e119f31e82320bca6e72781ee9f79d75", "job_title": "Baker-Hughes-Incorporated", "place_id": "ChIJcekacM_GQIYRPzL13cgQrPk", "address": "6919 Portwest Dr #100, Houston, TX 77024, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.47039, 29.655454], "type": "Point"}, "properties": {"photos": [{"width": 5312, "height": 2988, "html_attributions": ["<a href=\"https://maps.google.com/maps/contrib/101184977609161362375/photos\">aug4</a>"], "photo_reference": "CoQBdwAAAIMq5gZRtPF7ovzYmvjS2oidRMxMr2x9N1NBbWcJPSLbleLrNxSS03HGs4pCAaG85Cdmewd9f4mzF0AWvTvmBrRf75UJqV1kk8A9KGiQvH5me4cnVZa_RJeqpe1TsLgqoLJZEtpqwrEet62I8mmE04fBC5LC3OWGvN0dVqmFloluEhC-VMN6cJ-Jn7TUC1XqZ3mRGhSporxztSUaEA0gCsiQGlBSKS0rHg"}], "types": ["park", "point_of_interest", "establishment"], "reference": "CmRRAAAAvYvt72s_RhJLB25CEG60OKF7m4XOQ6fGF8mMDFEjKrzTrJk8ExrCVVgf4S-CqeIp8NGaOU5D6WIC7tRsdOLNXLmZP7La934P1r2fIpuCCqOTxv-oj6zUtD9vHTpqHGv_EhDgzCAIFIoV_TxBiN1V8d2EGhTz970Kl3KSw1yFJQjBUIr07hAJZg", "name": "Willow Waterhole Greenspace", "rating": 4.3, "id": "0127506e8071350c2d48f0ca56e939045297a0f4", "job_title": "Baker-Hughes-Incorporated", "place_id": "ChIJR6_2zTzqQIYRsA7wExgfDWs", "address": "S Willow Dr, Houston, TX 77035, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.4003322, 29.7388505], "type": "Point"}, "properties": {"photos": [{"width": 1136, "height": 640, "html_attributions": ["<a href=\"https://maps.google.com/maps/contrib/117056878997299689379/photos\">Marisol Brown</a>"], "photo_reference": "CoQBdwAAAA9RLJHyNYBB395SwyeF8h6M3mqJ9T9j_AxvZxSYEqCscNmZhEJmlh0imsu1ap41MKiNrP99hcXOtM-AwjNjeXZ6nMwTvb6xKzNmnuwGom2H9VhPQm0tHBU_IAZxR_u6qv7mPad9u4NKiwJzEmtnCd0alyJiFIsqAlLBjJaS9pxHEhCtUgNBOlrrrMCBq5EEGVkwGhSRvupdILiBeRYA1ARulqA5rHksBw"}], "types": ["point_of_interest", "establishment"], "reference": "CmRRAAAAIE48hwxd-khYAasgKXQPPQKBO0ZKz0xjv_BdEOswodRoO049rSdbtziKYr47u9v-QAqt_UUFNUO36KwYDiZ_9euBgnMZparNsMtgNvRQbpQfXuIpuJ5iEYFIl_FkW_hREhClkocMwArVLcAUFxoimNhLGhSFwEAb5VtJcnu6U7NLef42goaH7g", "name": "Masters Fine Art Conservation", "rating": 5, "id": "a462c2eef4e22ea319485ae7b84f3d20756cbdd1", "job_title": "Baker-Hughes-Incorporated", "place_id": "ChIJp8u2bZvAQIYRbosnWz6cVmY", "address": "1612 W Alabama St, Houston, TX 77006, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.3876169, 29.794149], "type": "Point"}, "properties": {"photos": [], "types": ["art_gallery", "point_of_interest", "establishment"], "reference": "CmRRAAAA7ZngkmyuyasghCGzk42Q82sIvJyEx6PopNMbxkYQRKDzkAY1WT_jiEiKFyiGB7vTBkbZ5d6tmni0qUE2ESNv5-_H8NHkvWqrahkEKuA1rvLe5Ghns-0iBKdFltViwZfqEhCUp_977EmQRbvm2vHTlXQ9GhQw1eVC6CmdOpVLGobsT-I-De-sBQ", "name": "Whitten & Proctor Fine Art Conservation", "rating": "NA", "id": "883a8c5ef35ab28e1630235ad65a6b16506a67fa", "job_title": "Baker-Hughes-Incorporated", "place_id": "ChIJ8YuXE6K4QIYRn1SF1hazFEw", "address": "1236 Studewood St, Houston, TX 77008, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.3858767, 29.7300997], "type": "Point"}, "properties": {"photos": [], "types": ["point_of_interest", "establishment"], "reference": "CmRSAAAAOcg1FTaXZ-vsxly7_zwuR_CySVkH0NOvPZpOyOg4VHiltpNk6uU-MwFdVoakJuK4LNXPSTS7yxKzytqt5acXcjNcSEQ8hOmx8tZLYTUOg0Q1HFvgPnkzbw5f9oNXeOtwEhBfGiT_UWICdyiBZSC1XHt3GhTUrl3HDtI-axAP4OeHvUzrk5VapQ", "name": "St Mark Fine Arts Conservation", "rating": 5, "id": "ea2d4bac6d74716b33f456dff3aae0cc0b43cca3", "job_title": "Baker-Hughes-Incorporated", "place_id": "ChIJKbDEoXm_QIYRcRFBlp0dE8A", "address": "4901 Main St, Houston, TX 77002, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.483218, 29.7482286], "type": "Point"}, "properties": {"photos": [], "types": ["point_of_interest", "establishment"], "reference": "CmRRAAAA_ItaKvtEjaNoxFFyOq2N8BimUgEnTtJOlw_j8GxaixnDrdGfl-dXw7byiKH6GZMdDsceQ1ByVVuGvgn90qbc3Vk_UHPWXcqgpYdM3UqFS-oTfSBgdmxQ6sM5s32ll1BbEhDK9pgM9nkbNKcn1je2MUflGhSuclZT4H66ufopnTM21WExt1NOxQ", "name": "The Nature Conservancy", "rating": "NA", "id": "90af6fb9fb926dde9f7103577cebc4150bbb1dec", "job_title": "Baker-Hughes-Incorporated", "place_id": "ChIJq-m4EX3AQIYRJkn4Lhccp2E", "address": "1800 Augusta Dr #240, Houston, TX 77057, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.42318089999999, 29.7345943], "type": "Point"}, "properties": {"photos": [{"width": 750, "height": 437, "html_attributions": ["<a href=\"https://maps.google.com/maps/contrib/106788706324997826205/photos\">Erika</a>"], "photo_reference": "CoQBdwAAAJWvvapoGhxRlK-a-EWimVcvSO4bxHXYSXOY4itMyt70HXCTrAHkzLsXdhjKOP_x_bIXuEhWcS-hwY2--zjQj2MBrQckBXYMfOP-CiKD4L3UUmewndJcdZPfof2SZUkBCQfxxc1i9yDzT6olk8TiNc6XTcRfTwDPumlDYak2Os6WEhASwN-ORVVb_FTI9Vj9OJS2GhQ-MoJoO75aFAlNg9XdC4JNlnLnDw"}], "types": ["point_of_interest", "establishment"], "reference": "CmRRAAAAXDFhP-BOwZ6pjvzP8gqRpsMCEzON2wkD8Ub5lpYfEJCDV4orq9-FUPl95wSYvj0FyM0JQ09Ul7hYOror0XQm7HFRntKF4JCvHOnNqRG2YesssbUTFD9k73WvDdm-M8tcEhBAR-pTHZedH-W6XmUE8xE3GhTjWjaHP6B-OqqvSxnsyQz4Y2CvLQ", "name": "Student Conservation Association", "rating": "NA", "id": "1c5ea7722fc0d99e9f7dfca55f5d9078224d51d3", "job_title": "Baker-Hughes-Incorporated", "place_id": "ChIJQcqBXfDAQIYRErawO-goGj4", "address": "2990 Richmond Ave Suite #400, Houston, TX 77098, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-96.038102, 30.055621], "type": "Point"}, "properties": {"photos": [{"width": 984, "height": 985, "html_attributions": ["<a href=\"https://maps.google.com/maps/contrib/110279808588468038448/photos\">Peckerwood Garden Conservation Foundation</a>"], "photo_reference": "CoQBdwAAAIqyo334ifUYjCAc-o4FCLYXpewz6ywCtVIHTqtcCDObz1ZlCCOKSSaJY2FYfTNVWKMqSOYJCxp87oZxmPKAKBfHmO6Fkn7L9rAFVfNUuf9muyaywib1Du5aaoJJRUOoujvLuY8l5sHuSggbTyi-bibhnKQWDtE34_tLgzgIG1q3EhAnAtSHwH8hnSRTp5QGlZ86GhSf2M6ZwqKSvSIO5MoV2xrP4DGuKw"}], "types": ["park", "point_of_interest", "establishment"], "reference": "CmRRAAAAdXVCUmUY7IKzTkz23WDGMdWPrvb2aKlPe00wOugrcKsCW47oMGaAGHhY6XoRd6hAEkFXXGXrB_luGJ3uTIg-9EALdjkKqPePgJPGdtci5kR6V08_yjhOnKm3UZLPn3Y5EhCT83Ne_No9K-5Dka4-l7UsGhS4MvIyrHnKjQAqTttvPTtZAqAZ9w", "name": "Peckerwood Garden Conservation Foundation", "rating": "NA", "id": "e618a4c618cd67ce4f5fdc165f640220ab3b53b2", "job_title": "Baker-Hughes-Incorporated", "place_id": "ChIJmUR7pvHKRoYRIIl0o73bPGE", "address": "20559 Fm 359 Rd, Pine Island, TX 77445, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.64386449999999, 29.7515036], "type": "Point"}, "properties": {"photos": [], "types": ["point_of_interest", "establishment"], "reference": "CmRRAAAAIVFc0utMD3gh9mGwtBLg-9lLWh10aPoJFdbP7Qoi2J-SKYmsgO9zzb7nBId3hitsyfKsJyKgtY8rCM9ja3p3LzWh09iiGr-6lG8IArW4psveF2E5-rjDNPoNDuxfRaATEhDxmhiG1F7Bsk8hFusskaPkGhQ8bA8uEgPEfsQCF43aNuTlplYhtw", "name": "H2O Conservation Technology", "rating": "NA", "id": "30c07988ef8dfc62dac712b9d587daa4a36f2539", "job_title": "Baker-Hughes-Incorporated", "place_id": "ChIJIWZRKeHKQIYRXxta3wOMGGc", "address": "1725 Hwy 6, Houston, TX 77077, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.5705632, 29.7714443], "type": "Point"}, "properties": {"photos": [{"width": 3024, "height": 4032, "html_attributions": ["<a href=\"https://maps.google.com/maps/contrib/108143329814504597326/photos\">State from Jake farm</a>"], "photo_reference": "CoQBdwAAAIj38EJQUdN3QkQ4QAkWcMDhJnPJlZW2DSlkpO88KgD8NM0ExILkX_rxfF84DTokPLO-MMx-LVoSVpiqdn0tbdN28Og0MPxyavQuGK8xp4mri-sCvu2J9G-6wU2pnD7rsxQE2Qh6IKbFA8i7C5uC3wGA5Lfs6Kx_BUo5zZCRTz6gEhAICEVLRe38rVboKjdSiSdEGhRF5y-DRShQn4DqDjuJ5giTwcZHTw"}], "types": ["park", "point_of_interest", "establishment"], "reference": "CmRSAAAAjD5wTmV6XDbvE1zYr_iEwONkV22M-CDEZpNlJXtTsCrw_7jb4Y-mmKcmtUJgx3b6BxnMMHdIpR7xk48ZW3Xb1sTdVpmRMtG9QvTU1XUGGgMj2Soum7LACAClarwiYX76EhCPcHKnNUoABWqLWot1kwzkGhS89CBx2yFIb419prS7GoUYJkYhOw", "name": "Houston Audubon Society", "rating": 5, "id": "050a5458d86bdd1cee7b09678bd6256d0a20a73e", "job_title": "Baker-Hughes-Incorporated", "place_id": "ChIJlQOxwVDbQIYR2uX_TZl0TYc", "address": "440 Wilchester Blvd, Houston, TX 77079, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.56820189999999, 29.770778], "type": "Point"}, "properties": {"photos": [{"width": 1800, "height": 1200, "html_attributions": ["<a href=\"https://maps.google.com/maps/contrib/108765250995932379967/photos\">Audubon Docent Guild</a>"], "photo_reference": "CoQBdwAAAKa_-PAAIbMUH98ch7pJ1VPnklvTNS6Z8GuEdVqgnLNEp_PC98vsQhJdnU_FKrGjMJflFHk2IOUGJxMIX3dCoCZ1VRHOzeEBVhi4i-FED_u-d4RLtBPxhjROCNTvr55p0crsne8R3b7o8KTq6GbGXGfd4MwAz8eJjw2Q08ciFL5rEhAA5xLDHFXT9FjmpqkrFt43GhRSa7Lp-7tFPkzVgfvw5MF2eq7zWQ"}], "types": ["park", "point_of_interest", "establishment"], "reference": "CmRSAAAAWogffBXUD1ZGYk__K39HNhbSO_HYpKd-HGfJiXFTEQT9A6s3hF7fjqgNdODHqqkRkSA6FyRQ3yHP-wiXlOOytStFc77sa3Z5JThm_FyiGyauHhxYK640izO_TA0HN0GjEhATYn5G4zypJ58IbljKm8K_GhR4bM2k3vgmq19hDg0InHCUMUn3gQ", "name": "Audubon Docent Guild", "rating": 5, "id": "7ddd5daf76cc4979e2ba6b062322d1c77d5d1c07", "job_title": "Baker-Hughes-Incorporated", "place_id": "ChIJI9XyNFHbQIYRtwHb8EtTpeU", "address": "440 Wilchester Blvd, Houston, TX 77079, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.44932349999999, 29.7803218], "type": "Point"}, "properties": {"photos": [], "types": ["point_of_interest", "establishment"], "reference": "CmRSAAAAiAu29X2OV_WFXcJlRgdQUuo9SLEHeEVKmuDFXmiiMvFXROB9HvYUMWUP1ulDQp0jGynLiXJtaNrDKoycDe-kMAsnB6Hs7jyuQE3M2fkF1YpxqFTMgJxWDQLqxWxlgfr7EhBMhxh4sHXIvA2_kIfsq1PIGhRsC2RB9dR4Ww83h4474yaKnY6epA", "name": "Coastal Conservation Association-Tx", "rating": 3, "id": "7258b034e119f31e82320bca6e72781ee9f79d75", "job_title": "Exp", "place_id": "ChIJcekacM_GQIYRPzL13cgQrPk", "address": "6919 Portwest Dr #100, Houston, TX 77024, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.47039, 29.655454], "type": "Point"}, "properties": {"photos": [{"width": 5312, "height": 2988, "html_attributions": ["<a href=\"https://maps.google.com/maps/contrib/101184977609161362375/photos\">aug4</a>"], "photo_reference": "CoQBdwAAAOK0ypYHPocax7p67iW8P6LFaLKGRcTE--HZp0mwezkizeL7wnTSo69VdGxdSXoE_gHA8xwqN6bRgGFSuaUX0NtLuGcjoIaczAou9ZFAVfHGyCL9Edz6E4neKWTBK_DLO1UGOgMYjiuK0ZI_e5kEGtUwTO70bSaIDOYx5VC5Ge9rEhAI2WKZQujbZAXv4AejaS2LGhSaan1zOZTaHghv2XfBZ1yj2dtGGA"}], "types": ["park", "point_of_interest", "establishment"], "reference": "CmRRAAAAIjKY3STD3nVOcfJGrYP5wKiRpYLhwbL9XiM0nFXgoLPzKf7pBN9llRZHAybDYi8ftZdPZuftbHZhrSMA075ygOW-vKv2QHQAgH4WRGGZSenPEn7IOc76w-MYadFIWSzGEhDJg7zSeqAGhbJeS98W6habGhQqUFsIV7JEpP2lwMUGh6yXiWQ0cw", "name": "Willow Waterhole Greenspace", "rating": 4.3, "id": "0127506e8071350c2d48f0ca56e939045297a0f4", "job_title": "Exp", "place_id": "ChIJR6_2zTzqQIYRsA7wExgfDWs", "address": "S Willow Dr, Houston, TX 77035, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.4003322, 29.7388505], "type": "Point"}, "properties": {"photos": [{"width": 1136, "height": 640, "html_attributions": ["<a href=\"https://maps.google.com/maps/contrib/117056878997299689379/photos\">Marisol Brown</a>"], "photo_reference": "CoQBdwAAAA6JGLg-5lSPqZ4MvqW_PFSnzMDHKmyDQVeHDozsYg7mZ3CC2mZFJAxPeS_KDMWHit-CNaA17xVqVZEoNKgHPLnOsQOAe8bWXTPS22AqzGBAqs49BXeiCorGtydRwB8j-GFoy8b6utvaK3vQAorp03nKAL378plGPIazW__x4oB3EhAs51E-OC705W2mH6bSSSM_GhQCVrl3dihHJMgUrKIExH3sAcOaqQ"}], "types": ["point_of_interest", "establishment"], "reference": "CmRRAAAAsW6R8ohd5O4_RJQGB3WHYBlb5i1k9aNkk9PexvZQTEfTpS5c6I1o_DZYWIv3DhtfYlMnKWOiSqK7cO0BLsNYCUSuzsYNBZi5OIdhiUDEJmxAIMFzYbVj9fg2i6vIEdjuEhAzLKKdv7VS7qm34qjhdsooGhRtuKuhIHBso6QQu-5aGgQPOKv9WQ", "name": "Masters Fine Art Conservation", "rating": 5, "id": "a462c2eef4e22ea319485ae7b84f3d20756cbdd1", "job_title": "Exp", "place_id": "ChIJp8u2bZvAQIYRbosnWz6cVmY", "address": "1612 W Alabama St, Houston, TX 77006, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.3876169, 29.794149], "type": "Point"}, "properties": {"photos": [], "types": ["art_gallery", "point_of_interest", "establishment"], "reference": "CmRRAAAAybILRyN6Rx3a7a3to2rk3nUNKhvqC1gSb46vweeud3FU6iifjGlwlK89re3Svv7beIbAPJzbqavC_tRUFzgAq2R5K_uhhpb6fnZKoVEIofygaIegn0UjzVlzkhl1aEaqEhASi-jdYVOgjfcI-M1NFHuSGhSSDz7_CqC9F2hfEc6UJJiCoj4Dpg", "name": "Whitten & Proctor Fine Art Conservation", "rating": "NA", "id": "883a8c5ef35ab28e1630235ad65a6b16506a67fa", "job_title": "Exp", "place_id": "ChIJ8YuXE6K4QIYRn1SF1hazFEw", "address": "1236 Studewood St, Houston, TX 77008, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.3858767, 29.7300997], "type": "Point"}, "properties": {"photos": [], "types": ["point_of_interest", "establishment"], "reference": "CmRSAAAAA-CNqupUd3FE_IXa6EIc-R9Eayrz-0EkATXaKvOjfTUPjoKbobJToWP8uWvxLZV9RokKzusUJcpoQLHDDxrxBvs9klB6KdAoXtEKvhZDpt2heQZB3I2TZddTUNdZyd4lEhBJyVX17OQESeUCkZjlYIkSGhTfLrQvxFi9jdUT_1uRlt4sHJwb_g", "name": "St Mark Fine Arts Conservation", "rating": 5, "id": "ea2d4bac6d74716b33f456dff3aae0cc0b43cca3", "job_title": "Exp", "place_id": "ChIJKbDEoXm_QIYRcRFBlp0dE8A", "address": "4901 Main St, Houston, TX 77002, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.483218, 29.7482286], "type": "Point"}, "properties": {"photos": [], "types": ["point_of_interest", "establishment"], "reference": "CmRRAAAApjjT4HCuycn449yE0HuiflY2Yj6zOJoO9CGfPKwALy8QDUFR7TmknleM9VyM_PtouGXLUEW3S8F66LJeIDFMxr5khurNsIsNGtdhK3Aazab59khmwzpbM1DlcAQGgX7mEhDS0dGiEoEjZvm0eWL0sRJvGhSnjp5yPc_8BJ3FErF2-WnZEsR0kQ", "name": "The Nature Conservancy", "rating": "NA", "id": "90af6fb9fb926dde9f7103577cebc4150bbb1dec", "job_title": "Exp", "place_id": "ChIJq-m4EX3AQIYRJkn4Lhccp2E", "address": "1800 Augusta Dr #240, Houston, TX 77057, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.42318089999999, 29.7345943], "type": "Point"}, "properties": {"photos": [{"width": 750, "height": 437, "html_attributions": ["<a href=\"https://maps.google.com/maps/contrib/106788706324997826205/photos\">Erika</a>"], "photo_reference": "CoQBdwAAANtzobIbNUxJt0sHY5R9LdCy16i7vtMU-57wmyoo1q0cRadELM-nsMxHnN33IPRs5bMYOrbToHHKvwiJyu5VaJoKKawAKzvwU6330pYwm0O-LQJPmgJ7ma_WKtxppKVhGX3JkxniI7NMw0gjquv6NxVZs8_EF68M346vXadqe-C9EhAtDFHEULSrBRA4XxSCbJB9GhS9hK_tyAiaYv--f7UysTyU1t0zIg"}], "types": ["point_of_interest", "establishment"], "reference": "CmRRAAAAPOIT15P4GNXAfMBfuyLRVidWjID7aQpeltKLZm298RvhOAkZ9mj-rxc8OIrRraDtjq6pf_qg3s7rKsOIjQV4-9jLd8Xkm7YWyP_3QRKIHhR8OYboMEPFUemAmlOO_g6kEhCpl6YsAKQb53tNDnjQuCj8GhRjm7ArzKGCHJ1UZKIa2P8uNuVjsg", "name": "Student Conservation Association", "rating": "NA", "id": "1c5ea7722fc0d99e9f7dfca55f5d9078224d51d3", "job_title": "Exp", "place_id": "ChIJQcqBXfDAQIYRErawO-goGj4", "address": "2990 Richmond Ave Suite #400, Houston, TX 77098, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-96.038102, 30.055621], "type": "Point"}, "properties": {"photos": [{"width": 984, "height": 985, "html_attributions": ["<a href=\"https://maps.google.com/maps/contrib/110279808588468038448/photos\">Peckerwood Garden Conservation Foundation</a>"], "photo_reference": "CoQBdwAAAPheDpj35HOm4UnhKu8mxLAMsdXOirVbPXGXqJ5NHsePiOOmnLvrcwWjsxac5o4UzvaUYwLXQnHRLnP5zJ4QsuytPu27MpRM9MBlPwfiDO34hxkUVusjl75BCs7WM3KnKTxxYJMVKc0XsRL0sfKjcybxbw4yhjuEUIPq_Uu_tguyEhBqldDreJ5MzEO5ghx8UpgiGhTA_sCe_SEQsA0lgrxGqq1Wdp2Zww"}], "types": ["park", "point_of_interest", "establishment"], "reference": "CmRRAAAAanel8gvEPmFRhLuE_HvXekhnfvCpK_Ymb1X9bQxj9_DJuNQb6sfJVwyh-f_SEypzqhfPaD2lmUSSKo3kZ71jICYiO3UsXqaqqzDf_Z7U4BxI1WYY-SA0Xp5aRC03pkrCEhCnqoyzfzvgYhXtKxCcOeJMGhQgnvjNhiHvxqw7s0eupAj4ZQaG8w", "name": "Peckerwood Garden Conservation Foundation", "rating": "NA", "id": "e618a4c618cd67ce4f5fdc165f640220ab3b53b2", "job_title": "Exp", "place_id": "ChIJmUR7pvHKRoYRIIl0o73bPGE", "address": "20559 Fm 359 Rd, Pine Island, TX 77445, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.64386449999999, 29.7515036], "type": "Point"}, "properties": {"photos": [], "types": ["point_of_interest", "establishment"], "reference": "CmRRAAAAxc2_ShsPrA05AgPDXsOn7In4shKXG5n60ND6SE5eb44H4s3m2cii3at8cdErKd-2slUrhu2Q1R1dwmBACMLEwrhzKpU_VeJ8i5tgIV_JwHO8bYVtNka1u8y07Im0xqgVEhDsqPeLad-RL3Gc3ST0BOOfGhSkz2_B0HRTmL-XiuJ-tVBdsS_Tzw", "name": "H2O Conservation Technology", "rating": "NA", "id": "30c07988ef8dfc62dac712b9d587daa4a36f2539", "job_title": "Exp", "place_id": "ChIJIWZRKeHKQIYRXxta3wOMGGc", "address": "1725 Hwy 6, Houston, TX 77077, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.5705632, 29.7714443], "type": "Point"}, "properties": {"photos": [{"width": 3024, "height": 4032, "html_attributions": ["<a href=\"https://maps.google.com/maps/contrib/108143329814504597326/photos\">State from Jake farm</a>"], "photo_reference": "CoQBdwAAAA2pLxq--4H_PARMk1PDYd6z3qU7-Pkls1dcb8-eySNXiRBRyNzkEovuITUXVviu0r4YFCD6Mk11k7-BwG-MKmaghJE6j3qPhZF0BjQk45uAQuZCMzDMYvJKgSjWc7kVSfgeXGMKWakkfsepx1fEJlXj1BgNwgLpTpw0d-UixPWkEhBua-HZqzZtsfwvTzpTIX4wGhQvT7_j_KtoRr-fQ5Pv04PprpRu_w"}], "types": ["park", "point_of_interest", "establishment"], "reference": "CmRSAAAAXwnep-Yh9rVnhWOJHLO6EqTkgGgGe6RGzSZzWUkVlDJWYkKstFmn9p48L3aZRlgVmDq51-8-nj4qC2Rv82R3yJvmPC1xyLh3V0ph5f-r9jRfCOW8qEqqs6CLU_rf6CX1EhBhEEA2wLddtPByK1-C1kH2GhTZSKPehtyBKHOYF6RoPB-7tmQHpg", "name": "Houston Audubon Society", "rating": 5, "id": "050a5458d86bdd1cee7b09678bd6256d0a20a73e", "job_title": "Exp", "place_id": "ChIJlQOxwVDbQIYR2uX_TZl0TYc", "address": "440 Wilchester Blvd, Houston, TX 77079, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.56820189999999, 29.770778], "type": "Point"}, "properties": {"photos": [{"width": 1800, "height": 1200, "html_attributions": ["<a href=\"https://maps.google.com/maps/contrib/108765250995932379967/photos\">Audubon Docent Guild</a>"], "photo_reference": "CoQBdwAAALokM8wGG1stLL5IuXP1IuobCqMv--vmpFoson-eXSWgGYmBI5Tgsu24_-9-QcePewGRPLhZM1SVXxV6d6m7NrhADfwhcOkgXT15blY5Ep_Bw_vK5CkyHuKL78dImzafdL-FNWOHg2OiNAykakc8e8m8aLVWd36zB58BQ8GPqMvJEhDfKpakjpnWFp180dYk3K1oGhScVsXGh6LKv7b0JoaSKstZpwT2ig"}], "types": ["park", "point_of_interest", "establishment"], "reference": "CmRSAAAAbvp3sesRj-GUK7Sf0M47rcIEJHo5cl-1br0-g-bVHE3x8uDkR5d-uIvmLFW753bfx0-kUsC3PH_wu-DysfuusTffdqOnrCRicb2zAbIYbsnFLJ5uuCnhe_aHZ4jtz8mDEhC5BOL91ifJvUwQbnLjp619GhQQKWNVW4jaujjTo3J4UD4JUNaKZw", "name": "Audubon Docent Guild", "rating": 5, "id": "7ddd5daf76cc4979e2ba6b062322d1c77d5d1c07", "job_title": "Exp", "place_id": "ChIJI9XyNFHbQIYRtwHb8EtTpeU", "address": "440 Wilchester Blvd, Houston, TX 77079, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.44932349999999, 29.7803218], "type": "Point"}, "properties": {"photos": [], "types": ["point_of_interest", "establishment"], "reference": "CmRSAAAAAe1q-OgkqF3fIhdgkGUVCdggEhfjXroTMEOJ9UHUvwdyZa_Bnc7eW07M_5axhS5LYWpJX9hVDh7hDv6-b-sI6pzl5pqeNtwbrnYkyYdISFl-o1A5DdFlAvT0nrYpNkH5EhAHehE9GIg4cR1tEkdJ_b5vGhSWE9lIE2B1amyqzwCF07-iG7u51w", "name": "Coastal Conservation Association-Tx", "rating": 3, "id": "7258b034e119f31e82320bca6e72781ee9f79d75", "job_title": "Clean-Harbors", "place_id": "ChIJcekacM_GQIYRPzL13cgQrPk", "address": "6919 Portwest Dr #100, Houston, TX 77024, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.47039, 29.655454], "type": "Point"}, "properties": {"photos": [{"width": 5312, "height": 2988, "html_attributions": ["<a href=\"https://maps.google.com/maps/contrib/101184977609161362375/photos\">aug4</a>"], "photo_reference": "CoQBdwAAAP3KEQBQ_aN3xGCU4SXkwWqOMFZwkspQNDd9T8wRuxdRp8F8fGbWvD7O9suxvpvfXTIaRUiWpz6DNdbW3Q8_pfmL2sJEWosPKtJbiOJfGY4oxnKvYYHytPg3WLsbEYw2TpeIv6QjjVR46rpS_9WHvyyZGeS4U-WEU41Y7R0leQr5EhAHuiXXJ0SpUJ2tTmQgjRy4GhQzsw0bNXgbUiR0z_WW4CruWd7-3g"}], "types": ["park", "point_of_interest", "establishment"], "reference": "CmRRAAAA51We6YP1521sflwW1TQ4nW7oZQ7FhxipLE7xIRzLk5JRz9DOY_2CFEOMEXREo-Kw7LTiaBXZuXQb8i_RQZfoaXdwUVGVLn25hiXqEP0JFJFXptYi15Vweaq_BMqU0ncaEhAH1lvEC1RArUNXKdHMS4cGGhS93U7A1YHbV10b6Wmc_oHQLtPRAw", "name": "Willow Waterhole Greenspace", "rating": 4.3, "id": "0127506e8071350c2d48f0ca56e939045297a0f4", "job_title": "Clean-Harbors", "place_id": "ChIJR6_2zTzqQIYRsA7wExgfDWs", "address": "S Willow Dr, Houston, TX 77035, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.4003322, 29.7388505], "type": "Point"}, "properties": {"photos": [{"width": 1136, "height": 640, "html_attributions": ["<a href=\"https://maps.google.com/maps/contrib/117056878997299689379/photos\">Marisol Brown</a>"], "photo_reference": "CoQBdwAAAKPLhHDdoCk8YpA4mVD5uUCAdbmqNkkBD3oFff7wDShHgL2kWUX5ZEl28E9Ev6wy-eGRxssIdULuf2tlvnKUaKtl2APKl9YxypP2VFe6bZZKwCyN5VvtxdEa0LCytwu4Ul-xH2qypl4-XGxxvHq5HS3cG0QESMnRpRY8Ue7N59kGEhBS5SyNKxtQkyD7JySv3hBbGhRqeJ6jTyrv1-tAOL0k6OIMrUdnDA"}], "types": ["point_of_interest", "establishment"], "reference": "CmRRAAAA-iDVN6w9W8FahObgt3hIBJUmf_xqR_8aureVE4Ho1wHpt6lUBOOJJs1pmqg3Rxa6m65AZT6HLO1DMdUhqVYThyBKhr_bFaoMYy_vBAJXOKT1N6G8PrpS1uO3MFK_n623EhDH4JJNICLLuE4CPvD-saxqGhSEsz5AHC7lHqB3cH7URf_ZImMnUg", "name": "Masters Fine Art Conservation", "rating": 5, "id": "a462c2eef4e22ea319485ae7b84f3d20756cbdd1", "job_title": "Clean-Harbors", "place_id": "ChIJp8u2bZvAQIYRbosnWz6cVmY", "address": "1612 W Alabama St, Houston, TX 77006, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.3876169, 29.794149], "type": "Point"}, "properties": {"photos": [], "types": ["art_gallery", "point_of_interest", "establishment"], "reference": "CmRRAAAAPxHyrJ8WAOt7FhunEcmR0TkQNQS_b36tlAeYVFEv88pmfSt0KDKLR9gDzJgA2FhecyZ02ke83nW54SAu3GMdK-8kEISsjjDEusjednU-NPxXxcGIC1bH3AZ2Are19bYSEhChGPbp2PWUPQrx-hk5qmRWGhRuhvueUIxUvazQqPqoCyc1wCGKew", "name": "Whitten & Proctor Fine Art Conservation", "rating": "NA", "id": "883a8c5ef35ab28e1630235ad65a6b16506a67fa", "job_title": "Clean-Harbors", "place_id": "ChIJ8YuXE6K4QIYRn1SF1hazFEw", "address": "1236 Studewood St, Houston, TX 77008, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.3858767, 29.7300997], "type": "Point"}, "properties": {"photos": [], "types": ["point_of_interest", "establishment"], "reference": "CmRSAAAAXNifNTy6AVcHrIV7diBHHP4PHTckPGFQl8s7RFSVdUnk6uJYfBbbq7A3MSRqWbNKptaM0btcBhBuMM1-h3D077Rwk0d-aBLD5GI3cbk2E_LBpkc3jFKMRsxsSRzwzK8SEhANrkhnTu9jxooUY4pzZ6WNGhQ0dQkpgUrRD0Ad-0hNm3SRyfdm5A", "name": "St Mark Fine Arts Conservation", "rating": 5, "id": "ea2d4bac6d74716b33f456dff3aae0cc0b43cca3", "job_title": "Clean-Harbors", "place_id": "ChIJKbDEoXm_QIYRcRFBlp0dE8A", "address": "4901 Main St, Houston, TX 77002, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.483218, 29.7482286], "type": "Point"}, "properties": {"photos": [], "types": ["point_of_interest", "establishment"], "reference": "CmRRAAAAA_nHgp9MJR9H3crhLTfftOMZFb8KfHdwPkwmu0jyaBvwwBdU_nB_H1nc9kgcUNcUX4WeGaSpEcWS_udXfKcSS__iQ332EIsmG_8vzNCPA0LUjrZoWUr58Cxw9QYLoptiEhBz8LV2GWUzOQajsVDJBc1wGhQ6bj_-8awn28YeCSAfAnspa8h2WA", "name": "The Nature Conservancy", "rating": "NA", "id": "90af6fb9fb926dde9f7103577cebc4150bbb1dec", "job_title": "Clean-Harbors", "place_id": "ChIJq-m4EX3AQIYRJkn4Lhccp2E", "address": "1800 Augusta Dr #240, Houston, TX 77057, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.42318089999999, 29.7345943], "type": "Point"}, "properties": {"photos": [{"width": 750, "height": 437, "html_attributions": ["<a href=\"https://maps.google.com/maps/contrib/106788706324997826205/photos\">Erika</a>"], "photo_reference": "CoQBdwAAAPvClFeWz56kAXgGuusS5L_Yw7PhYB_jHL_9Z87ClmbKCduw1IMTNxMxs2cm_iMaRupqD3cZRUpPXIJPMVXha2yRNL48Gr-HRrbEzlFTIOHFOPGx-5crmTiNLYriE7iXz5AzlSwTU59ru8xRCr9rVPuh0ly0cIq21C_r2hh7-iMAEhCe2wdULmCAv_mFX2-Bu7ZlGhRLNZE2cxMfQA0pJa-UazbdJoWVfg"}], "types": ["point_of_interest", "establishment"], "reference": "CmRRAAAApCjDkBR5ZGIDIe9qzamhMQnr0UfgfwJJV4EJMkSSd9V9PzkPgt4JtcCmCYruBDPMRf5qj0umGMjlmQ6Y7RiQ_7LT7SsGg4koY9p4TeamH4BZnS8G_BhDSpMXtXI4koUSEhDUMYtntuMlulxshSYwaAeQGhTePlGyeofHbS7KEkftCJfYHYZoSg", "name": "Student Conservation Association", "rating": "NA", "id": "1c5ea7722fc0d99e9f7dfca55f5d9078224d51d3", "job_title": "Clean-Harbors", "place_id": "ChIJQcqBXfDAQIYRErawO-goGj4", "address": "2990 Richmond Ave Suite #400, Houston, TX 77098, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-96.038102, 30.055621], "type": "Point"}, "properties": {"photos": [{"width": 984, "height": 985, "html_attributions": ["<a href=\"https://maps.google.com/maps/contrib/110279808588468038448/photos\">Peckerwood Garden Conservation Foundation</a>"], "photo_reference": "CoQBdwAAANXY6akqmZUxNVaPpTe5agHZy5pvh3dfj_0ifu1QQejhhMhxHqy5-4awT2NqFSe2ul6DQxeSDA8RmL0ctirqOXdG6P7EQLIpHzvd74vW3qe4IWY02zJ6Mr4zWU5BJwX4BSo-TwGzJUf7omUXtqXiW4uOLvcYVXL1kgde89FO0kW-EhAedQayQ3fuQQgmfsaLXF18GhS3rGbUNKrTKEhDrTCQYMLwdGX47g"}], "types": ["park", "point_of_interest", "establishment"], "reference": "CmRRAAAAQU6CNbv_5bk564gohE0qsPiRE8-kWjOtWUeEeGgjK4srhA5HoJmAemDbtutFdh9qy3GIbJ0rxvMtmloyjuOLL-JyjmK6-_NoeX_x46mElNCIfyjtlkQK9SXMuBCXkwewEhAJoi8wYxyxP2vwCXolRFczGhTFOLJnlYLYr0whJzBDuCCZNX2brQ", "name": "Peckerwood Garden Conservation Foundation", "rating": "NA", "id": "e618a4c618cd67ce4f5fdc165f640220ab3b53b2", "job_title": "Clean-Harbors", "place_id": "ChIJmUR7pvHKRoYRIIl0o73bPGE", "address": "20559 Fm 359 Rd, Pine Island, TX 77445, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.64386449999999, 29.7515036], "type": "Point"}, "properties": {"photos": [], "types": ["point_of_interest", "establishment"], "reference": "CmRRAAAAbOdTxkSHO9ST4b32gHo7UBpotyWkGemTqwiwuz_nIHWE5mQH0P4rjTGttr4EDlKXsPP396q7OEFxmYZ1CV1MQlyVkHf48D7ZxAVJYgdwqLLLahz2QKRAyR7QZ2MuSZkMEhBKgFGtvnK2J93AIa5aQnqHGhQ4f49jR_qOTFOwmIeE_p9U61dLFA", "name": "H2O Conservation Technology", "rating": "NA", "id": "30c07988ef8dfc62dac712b9d587daa4a36f2539", "job_title": "Clean-Harbors", "place_id": "ChIJIWZRKeHKQIYRXxta3wOMGGc", "address": "1725 Hwy 6, Houston, TX 77077, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.5705632, 29.7714443], "type": "Point"}, "properties": {"photos": [{"width": 3024, "height": 4032, "html_attributions": ["<a href=\"https://maps.google.com/maps/contrib/108143329814504597326/photos\">State from Jake farm</a>"], "photo_reference": "CoQBdwAAAOJh7APStjkfUiVZE_guf_OZcUb-3U8Qp_bsOc2SsBVoTZ0iAEZQXEu4_-JRXMag48vJJVPBbEkoP6Ef5f_thExEEtiEF-_LX2ij8Z_STd6Rx7mfAlgnbSgWZHqLqGKLDMzMer9O_iXjtcG5ou2VmCcjbiPc_IKNJTckPSKvsJh3EhA0FYeEUaJHv0iv50n2-VLiGhSNRZeiY0QBOkieYCiotsddboPTtA"}], "types": ["park", "point_of_interest", "establishment"], "reference": "CmRSAAAAM83v6IzW8WDsup8EAqkzSUfT4rx8XZCsWnz0L8OBPDAHdlY2U_kZ4RLL6kHdlOluWHVJyuj-wZiruAVrgjIwC8ig0BSI5CyTQQKef3IXFgDrJfFZeT2JYWuJOXuaZ6CkEhD7exCccCXFDzcCgNzUop0lGhSXfijs7T-8OdIoDdeV4IcRZvBdSA", "name": "Houston Audubon Society", "rating": 5, "id": "050a5458d86bdd1cee7b09678bd6256d0a20a73e", "job_title": "Clean-Harbors", "place_id": "ChIJlQOxwVDbQIYR2uX_TZl0TYc", "address": "440 Wilchester Blvd, Houston, TX 77079, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.56820189999999, 29.770778], "type": "Point"}, "properties": {"photos": [{"width": 1800, "height": 1200, "html_attributions": ["<a href=\"https://maps.google.com/maps/contrib/108765250995932379967/photos\">Audubon Docent Guild</a>"], "photo_reference": "CoQBdwAAAOv0GxgJYUnGiI1ACq8i2edKUd3i0_R84T9ZXCBTnTZPZZgjbAC4iY-_Jy9pS58ohrRMHe39XC3HJItJxTU5Yuh7alg2AhA7w-Dng3VBvb4KLW9KJMpvGFGuVvGPOux1IVF4KFBFGBS5AoddAMK1xZ0_EQ7j-ew7SYkLwvCFgklcEhACpR8ulMBuP42X4FiZr175GhQkH6Udl4ORLdioarsXOHWYtX5Jtg"}], "types": ["park", "point_of_interest", "establishment"], "reference": "CmRSAAAAkycxep5-Zk_Zw6WBKVPHrP3BXaUMKcHF6X78tKz2_e7_cu3QKPztwbs5cy77TZTH5iAYIzCEQbMJLncdg9oZA6Ki3ZV3McfauoWg7K-99M-gmHutW58FdYLMortKrbz0EhBUdOKn1PCtF68Dv2WOjLTIGhSPxbVKgIKL_FAmzOGjf4ACoqpvHw", "name": "Audubon Docent Guild", "rating": 5, "id": "7ddd5daf76cc4979e2ba6b062322d1c77d5d1c07", "job_title": "Clean-Harbors", "place_id": "ChIJI9XyNFHbQIYRtwHb8EtTpeU", "address": "440 Wilchester Blvd, Houston, TX 77079, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.44932349999999, 29.7803218], "type": "Point"}, "properties": {"photos": [], "types": ["point_of_interest", "establishment"], "reference": "CmRSAAAAHoQ5L-sTmpRyo4JlUG9kymV9Z09xexTyaku9jMFWEjVLawNOzsTXMfZ7_ZzUFMqBuJQqqiz01sVK-6to-y3Fbg2AKpfdOYtTr5JIQM-Pd13I-wrLvJ5SuGpc2_GowaGLEhBJT6sicr1FzYBSfi7BMOqjGhSDXdFLyunQ7M7ixcCjPYqWxsU-_A", "name": "Coastal Conservation Association-Tx", "rating": 3, "id": "7258b034e119f31e82320bca6e72781ee9f79d75", "job_title": "Trc-Companies-Inc", "place_id": "ChIJcekacM_GQIYRPzL13cgQrPk", "address": "6919 Portwest Dr #100, Houston, TX 77024, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.47039, 29.655454], "type": "Point"}, "properties": {"photos": [{"width": 5312, "height": 2988, "html_attributions": ["<a href=\"https://maps.google.com/maps/contrib/101184977609161362375/photos\">aug4</a>"], "photo_reference": "CoQBdwAAADh90CPhz333IvDa-zo1w6xL4rfBQsg2531l3ycCWzEnXS1hSTSAls21R8q9rizjp_AMOUibAwKnXIkxNK0ol5-1xKabNDChwlj5LtiaLN0EsUVVfcNbCDBqZUgxpJrS_i2pIXMPr4T7TwNrAjQ6cXMtczwp8r4itKw-olXmP8JQEhC1_sZdncJvi--DLurTrAT8GhQjcwMDzeocTKsPwpOWNxk1BRCiCQ"}], "types": ["park", "point_of_interest", "establishment"], "reference": "CmRRAAAAAp92Z-J9SRdACHXQP9Q7hGk4mLfa180qUiTOg2V0y9_0E4sGB1ncxdSJ-ghl8EDOtaXmkwzO8JMmOu7zTap1C9ac_CLvynU0reQZqv_FxF7I-jYGK_0NQ_qhtV33dWFvEhDiFCT68KSp5MPVQWHRr3k5GhQUeheVcvh9I7tZ_JjGtaFKUleQjA", "name": "Willow Waterhole Greenspace", "rating": 4.3, "id": "0127506e8071350c2d48f0ca56e939045297a0f4", "job_title": "Trc-Companies-Inc", "place_id": "ChIJR6_2zTzqQIYRsA7wExgfDWs", "address": "S Willow Dr, Houston, TX 77035, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.4003322, 29.7388505], "type": "Point"}, "properties": {"photos": [{"width": 1136, "height": 640, "html_attributions": ["<a href=\"https://maps.google.com/maps/contrib/117056878997299689379/photos\">Marisol Brown</a>"], "photo_reference": "CoQBdwAAAGdZIU3_YdVOHuiGOQe7e1Vykm4VZ7rLzbxMzjsPRu2xIR62PVWxTHn_93d8u58BGfZKD8WLEeoA0OHnIdLhKamOXpnkE3yo_cPLxkiN8q5Ngm19Ykk8y9MhCdML1mg2dvt4h65UNbuXYjE9LoytkB8bVU_JWAm6Q8fsxnOnqXZHEhDMsM6ToiXzzB9Bn6twRY1GGhQ6O3cpLTV_04FYsmKhEz6lEJL2Ew"}], "types": ["point_of_interest", "establishment"], "reference": "CmRRAAAA46cGrZW7Z_kPmwhsohgNI_CDKDswDTLzU2x1-_GfO6npWwf8XbQbdjQPnkUvDuDDUT30gok_bCbr06JpFhzwqDugF9eGrM_anuMhhxBjFZe5ho8O62N3N7e5oaf8a2n0EhAvNuXKOq8iSpdpDT9vPjT-GhTUWKFZG4zzEmbkmUhcDGT5fFexXg", "name": "Masters Fine Art Conservation", "rating": 5, "id": "a462c2eef4e22ea319485ae7b84f3d20756cbdd1", "job_title": "Trc-Companies-Inc", "place_id": "ChIJp8u2bZvAQIYRbosnWz6cVmY", "address": "1612 W Alabama St, Houston, TX 77006, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.3876169, 29.794149], "type": "Point"}, "properties": {"photos": [], "types": ["art_gallery", "point_of_interest", "establishment"], "reference": "CmRRAAAAfIqvwAcz8aX9dChsu1tw6Qph4aQDRTvUOR10G5HsLRcRjuRx70tQbGzzn9bDDQl0YiuskiHhwFyonNey8yMX54FQl7Ufbpp_HjfEs2elhH2DKT7dTESNZt63pGUcXErhEhDiPbT7tL8m7sQptDA2qYbTGhSbpy94arYRHl_dXVk6WycrK9c2ag", "name": "Whitten & Proctor Fine Art Conservation", "rating": "NA", "id": "883a8c5ef35ab28e1630235ad65a6b16506a67fa", "job_title": "Trc-Companies-Inc", "place_id": "ChIJ8YuXE6K4QIYRn1SF1hazFEw", "address": "1236 Studewood St, Houston, TX 77008, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.3858767, 29.7300997], "type": "Point"}, "properties": {"photos": [], "types": ["point_of_interest", "establishment"], "reference": "CmRSAAAANRXdry1v5V-eZY7YN4w53XjjVeGurrmTjnzC28-sovphrZ_zKVGvsP5GQpGBW4WulRmNRgc3vz6JHugZfccugY3Ymcg549TXoAcpNlr-jsA2KxzFiMeNbbD6MCMt6ZVuEhCoe2zmA2H-YsdyK4QGaVNJGhQCn5zqZxaO_EZUZzeC-Br2yTxaMQ", "name": "St Mark Fine Arts Conservation", "rating": 5, "id": "ea2d4bac6d74716b33f456dff3aae0cc0b43cca3", "job_title": "Trc-Companies-Inc", "place_id": "ChIJKbDEoXm_QIYRcRFBlp0dE8A", "address": "4901 Main St, Houston, TX 77002, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.483218, 29.7482286], "type": "Point"}, "properties": {"photos": [], "types": ["point_of_interest", "establishment"], "reference": "CmRRAAAApIIQ4hers1T-Je-RwtEg3RdseEk3bNZv4FT8ZqMmEoPuTaI0hbXntN_lSr8i_AGvqT6rr3MQPPRwgzRgUS8yY2IK5rnPyo_4ZysUrptFuLn79bLqT3mBisNz73E-7CKLEhCjQeoKyHJhGUMT5CZIKw0LGhQuNStGE_Mf6Itnv9CQwzVcz4BSxw", "name": "The Nature Conservancy", "rating": "NA", "id": "90af6fb9fb926dde9f7103577cebc4150bbb1dec", "job_title": "Trc-Companies-Inc", "place_id": "ChIJq-m4EX3AQIYRJkn4Lhccp2E", "address": "1800 Augusta Dr #240, Houston, TX 77057, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.42318089999999, 29.7345943], "type": "Point"}, "properties": {"photos": [{"width": 750, "height": 437, "html_attributions": ["<a href=\"https://maps.google.com/maps/contrib/106788706324997826205/photos\">Erika</a>"], "photo_reference": "CoQBdwAAAJ8PbQZ_oe4wjYtHr4UpyOjNtym4EGBHpNGV0-GqfTjGxShkooZfnqgaqihIJ0ePxOlV4grbKdfVm2Md6vmhByS3jz6kuoWUzAenPP7oDd4gHMr1qCJSIlypf_jetRWV6MIzs8wNxXX0AxqdB1J3Q2mUMrPZhWMafxDCimd6Vv-cEhAmjSylHIDmcj-UHaPuUdv6GhSgl8ldCRVcoSS_XC4l377fulga1Q"}], "types": ["point_of_interest", "establishment"], "reference": "CmRRAAAAuY0Gf_Ci3eiW5TumqPkuMrUN3KIr7eQM-5f6Z9zM0oEmuMBTsOlgH76-N5YZSVI-_vL7X8fV0SKvCFZVS03buUOrdlRzjMA9byjJVFjKhDzcmaHKI7fHLiW-bjjZTD5CEhDfKvhTgGcOBhSaobuPP6V6GhSCQ0FGojCsgzCroZ55nfjEkoR1mg", "name": "Student Conservation Association", "rating": "NA", "id": "1c5ea7722fc0d99e9f7dfca55f5d9078224d51d3", "job_title": "Trc-Companies-Inc", "place_id": "ChIJQcqBXfDAQIYRErawO-goGj4", "address": "2990 Richmond Ave Suite #400, Houston, TX 77098, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-96.038102, 30.055621], "type": "Point"}, "properties": {"photos": [{"width": 984, "height": 985, "html_attributions": ["<a href=\"https://maps.google.com/maps/contrib/110279808588468038448/photos\">Peckerwood Garden Conservation Foundation</a>"], "photo_reference": "CoQBdwAAAChb1dJz5q9V5k7G7mDIjpZJ2IJtfrmN4xkQa7J5DewX7lfkOMIMDvseVXJuSoT-XLJbUwdLY0Tdsddg9Yd1fx-lO-q9h5pRHt1Z-c437uaPcbFarLYL5nRj5B7t5Zk-mCxvnbE8lxlOxwawzmg0LGHTQm8mDnQheu0YqidmulgbEhCed77gaOvFZxckki8KaN_gGhRcQ4_G_I4GS2iItWkeEARTZnJbUw"}], "types": ["park", "point_of_interest", "establishment"], "reference": "CmRRAAAAUxYSs26JbTMZZgz77mrWW229HaFz-eitn7aAO22BPCxWVFagr76wZWP4qqynXVYwD-n6fZZM_3skgVnRVkPsnjQ7j7_RTwsx0SIW7IJbFASUrb3eKK1vamj_QrklDNNLEhAUgUdsUtwclRIiD4H5AGFDGhSuV_gXrL3bpGIJkNNoO1w_vwv5GA", "name": "Peckerwood Garden Conservation Foundation", "rating": "NA", "id": "e618a4c618cd67ce4f5fdc165f640220ab3b53b2", "job_title": "Trc-Companies-Inc", "place_id": "ChIJmUR7pvHKRoYRIIl0o73bPGE", "address": "20559 Fm 359 Rd, Pine Island, TX 77445, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.64386449999999, 29.7515036], "type": "Point"}, "properties": {"photos": [], "types": ["point_of_interest", "establishment"], "reference": "CmRRAAAAcAGMAINP_09osg-l_yq-vLJvLJWzdWpIGUouGLRVRRvOZLmV-lvKMXprn9NxLJl4j45xKT-VvMaxT5fYB5FfQxZWha8MHE5QXFZJXC5gTDb8WgMilApTTgZjvpuosN8yEhDXrLkVI79Hrrtc4gTU7yH3GhTKYp4EeC6K-emt4S9qNn4LvJ5_AQ", "name": "H2O Conservation Technology", "rating": "NA", "id": "30c07988ef8dfc62dac712b9d587daa4a36f2539", "job_title": "Trc-Companies-Inc", "place_id": "ChIJIWZRKeHKQIYRXxta3wOMGGc", "address": "1725 Hwy 6, Houston, TX 77077, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.5705632, 29.7714443], "type": "Point"}, "properties": {"photos": [{"width": 3024, "height": 4032, "html_attributions": ["<a href=\"https://maps.google.com/maps/contrib/108143329814504597326/photos\">State from Jake farm</a>"], "photo_reference": "CoQBdwAAABTI97YTLM_sWEJyaT1pYtnnIfjBeAtpJOg8CiVm_vSNSnSpjVRcKXucOvoc_RJN9ayiYLWI80QrKxv0ZfWn3QK4akjrkYwf9X8g7J1LNx-msSBqwVciZ1KL9sckIsjmCuE6iwQA54J6TrAFyTgsae4FeW1mY2o-1sCmH5pLSzXUEhATgf_ugo1brnrF-RD17LQdGhSRz5aNbgBkedVrlOl0do5kkFGpVw"}], "types": ["park", "point_of_interest", "establishment"], "reference": "CmRSAAAAgrgvgCJ0WNwYYO5cwxJr81NzYc90h-VFT6XMAL940sz6C0HUe2gJtJYjQKUfJH4xg4VMmVPGgsZPI9jn7AnMlWCAjFRyQqIPVrLWhd_N30-IrhB7NLn7W91DtMGFMJIoEhDZ4Oybxwi55SKCQO-OTYo_GhRXYrxpdxsXRiBNh0_4f0bZ4drpGg", "name": "Houston Audubon Society", "rating": 5, "id": "050a5458d86bdd1cee7b09678bd6256d0a20a73e", "job_title": "Trc-Companies-Inc", "place_id": "ChIJlQOxwVDbQIYR2uX_TZl0TYc", "address": "440 Wilchester Blvd, Houston, TX 77079, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.56820189999999, 29.770778], "type": "Point"}, "properties": {"photos": [{"width": 1800, "height": 1200, "html_attributions": ["<a href=\"https://maps.google.com/maps/contrib/108765250995932379967/photos\">Audubon Docent Guild</a>"], "photo_reference": "CoQBdwAAABPBZuuzVC3tv5-fuBE7COf8Vexm3-9Pgm70161uE_kUixPtinEKTk5hZBo_Sh4sSOpbhAFhHZZFbmYwmZqEuNMeaurf7ICXEALxcPdfsV2bkacsj-9PlGAlbf71JV1B3Wm4c6qVTLusfnWtvUh8VlM0jeHoxE1sPPVm7JlRe8bsEhBWR0DfMV5V2BE3j2jbFzrIGhT0AwGPFoC70VbvPoYKD7gc4k3oCg"}], "types": ["park", "point_of_interest", "establishment"], "reference": "CmRSAAAAoi_r5kKXMWL_19MM3s9vIh8NLVV_I_C1j3ICWG7tL8PyIQNRKPu--kvndSGWfG1MbW-AR2dm7P4Kh6dj_8VjWew6XguuXWepbzszLlL8GwftxU0VSP4KXtddCb9NquSaEhDcaqoaV23q32BfDOj9FPTGGhRKwtgWq1nXm243OVu3pEuYZz0okw", "name": "Audubon Docent Guild", "rating": 5, "id": "7ddd5daf76cc4979e2ba6b062322d1c77d5d1c07", "job_title": "Trc-Companies-Inc", "place_id": "ChIJI9XyNFHbQIYRtwHb8EtTpeU", "address": "440 Wilchester Blvd, Houston, TX 77079, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.44932349999999, 29.7803218], "type": "Point"}, "properties": {"photos": [], "types": ["point_of_interest", "establishment"], "reference": "CmRSAAAAzvEF--QfhaLrQvwemufV1mgSb6en1jbbU1xwODx5H2K-JHXtK49rShjoxLGWRyH0VTXDgLK6shNIruhHxHacQ4ARKfL2fJJZdCgLzLvt4f9rL15q0zrBzrteFv7Gaot-EhDkvOiFm0dcnaYxfO9h2VMfGhQzJ6j4r6lvTKT7A4PKIiqQAP857Q", "name": "Coastal Conservation Association-Tx", "rating": 3, "id": "7258b034e119f31e82320bca6e72781ee9f79d75", "job_title": "Brightstar-Care---Sugar-Land%2C-Tx", "place_id": "ChIJcekacM_GQIYRPzL13cgQrPk", "address": "6919 Portwest Dr #100, Houston, TX 77024, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.47039, 29.655454], "type": "Point"}, "properties": {"photos": [{"width": 5312, "height": 2988, "html_attributions": ["<a href=\"https://maps.google.com/maps/contrib/101184977609161362375/photos\">aug4</a>"], "photo_reference": "CoQBdwAAAF3nv6Dr4q4gCq-difsUZ7NSj-3Sh7-WtHF_yh-9tN2oQ5kM8_BuK_QyDVySxIED3ciwpCc9NU-ap2oYVbPNUebq3TUqcw24LohAlsiOQ2Cdv-_Ryb9WMpSr-xrjt2YI3CTebM5RvkJRPVvnVJGh0Kjvi_UnfexByvbPtO6OtYWYEhAfrPY2yqi3rd_xbduScbfjGhS3keU_UYjNUZjLfGz1cip2GSuPug"}], "types": ["park", "point_of_interest", "establishment"], "reference": "CmRRAAAAztvuMPJ9rM7Qd8Y7fXoY-YITQ0HZGc2uJ0NH-DA0Z36_oqN7Jlb59G99QV5lFl1onOvKVYWUnW51FyhdeTFedNjGmrsvyK53QPnpb31kyhX5kC-outcJJMAH2piPA4ggEhAG83uF0PuolH6bAXgtEB_nGhTCikeLC5ysPGMQLKCEi8TNIADJxg", "name": "Willow Waterhole Greenspace", "rating": 4.3, "id": "0127506e8071350c2d48f0ca56e939045297a0f4", "job_title": "Brightstar-Care---Sugar-Land%2C-Tx", "place_id": "ChIJR6_2zTzqQIYRsA7wExgfDWs", "address": "S Willow Dr, Houston, TX 77035, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.4003322, 29.7388505], "type": "Point"}, "properties": {"photos": [{"width": 1136, "height": 640, "html_attributions": ["<a href=\"https://maps.google.com/maps/contrib/117056878997299689379/photos\">Marisol Brown</a>"], "photo_reference": "CoQBdwAAANejzyvwMjUkCrY7NYAXWNfwanpSuKUTae50AxDCnLJBD74O_69I6xaxvBZ0KHBlJyEJBLTCFTtU5ctYTaRhCDPQE4jiVTu-ezLKuYq4iyw_ybXx5irYgUEi56EPfjm5NA26dmXjtgLYZVOViMNDc2Ze_ZC_5Edb1YLQBAtFGkdEEhAj7q6mLP52JyRsK6AeUV4DGhRW5VB4KG5E-xxDKgHCUCOmGS78HA"}], "types": ["point_of_interest", "establishment"], "reference": "CmRRAAAAZkGaFabueRNYHUziLrky4I64prQIqI-JsU7bML3RNC_j-my2wQu8CaZy0H2l9U5qqC04L-XJ91J6z7wPeEgMfV4vHWfz8hLu3IEXtn28-9ZzbJrcQ7ebEvhhVxgqJuImEhAEXHC_8TlPq253H4HAVxgMGhRpkMuRQdNdl1dPru97fZonFqOZbg", "name": "Masters Fine Art Conservation", "rating": 5, "id": "a462c2eef4e22ea319485ae7b84f3d20756cbdd1", "job_title": "Brightstar-Care---Sugar-Land%2C-Tx", "place_id": "ChIJp8u2bZvAQIYRbosnWz6cVmY", "address": "1612 W Alabama St, Houston, TX 77006, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.3876169, 29.794149], "type": "Point"}, "properties": {"photos": [], "types": ["art_gallery", "point_of_interest", "establishment"], "reference": "CmRRAAAAiVo4W_EvJ2JstP5zx8GZeiLYLJKSJngxqFkmFfduqirK1zAIavKt8WnBe12ieBuSZupKUZAyY11vOWt1PFaGa16fo1N-L9YwvR7ECcgDpqloJwUfYBtE6GObPSjBG-ssEhCjdgNGR94BhrwLJK9kNO2XGhSG9DTKKvV8lZavKeLrYG_cuy7r8Q", "name": "Whitten & Proctor Fine Art Conservation", "rating": "NA", "id": "883a8c5ef35ab28e1630235ad65a6b16506a67fa", "job_title": "Brightstar-Care---Sugar-Land%2C-Tx", "place_id": "ChIJ8YuXE6K4QIYRn1SF1hazFEw", "address": "1236 Studewood St, Houston, TX 77008, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.3858767, 29.7300997], "type": "Point"}, "properties": {"photos": [], "types": ["point_of_interest", "establishment"], "reference": "CmRSAAAA_usE1zX0OjN2Jm45Ija5vECdhTQhUd9fB_6OO31icXSsaNNFDerIcoTHtid3AwLbaRiJ2ldE9tWduKvfhwb0GcR09hNhaYUZ6zASBjToRiTHbkjEl072J9ZWXlLFaqWeEhDKKUfFoa1IdW_bMR0TQ7PpGhSD5YjrLr77Gb3lBQSnZf031b_vFA", "name": "St Mark Fine Arts Conservation", "rating": 5, "id": "ea2d4bac6d74716b33f456dff3aae0cc0b43cca3", "job_title": "Brightstar-Care---Sugar-Land%2C-Tx", "place_id": "ChIJKbDEoXm_QIYRcRFBlp0dE8A", "address": "4901 Main St, Houston, TX 77002, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.483218, 29.7482286], "type": "Point"}, "properties": {"photos": [], "types": ["point_of_interest", "establishment"], "reference": "CmRRAAAAcTyl4mz8JewRw5c-qMPZ76PhF733yPxwdJWQYrjt___8b1E5PtzWdaCNMvnl0I0LW0NSgnN7F0pQ3sgMsBhipibB0ERsje2LYboekALfH9OCkB3E28TzKgV-KGhkffOlEhDCE9Utcp9AWzUs14M3K-LtGhQRNAK6lId0t_SjsxNjie0FbePrig", "name": "The Nature Conservancy", "rating": "NA", "id": "90af6fb9fb926dde9f7103577cebc4150bbb1dec", "job_title": "Brightstar-Care---Sugar-Land%2C-Tx", "place_id": "ChIJq-m4EX3AQIYRJkn4Lhccp2E", "address": "1800 Augusta Dr #240, Houston, TX 77057, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.42318089999999, 29.7345943], "type": "Point"}, "properties": {"photos": [{"width": 750, "height": 437, "html_attributions": ["<a href=\"https://maps.google.com/maps/contrib/106788706324997826205/photos\">Erika</a>"], "photo_reference": "CoQBdwAAAPcQR_xaJ1j6LP_CHghgmvNzUBgsd5my6QxXYru7_Uckd88W8685IlaOq_iAKsik_039Aha-irz-YiY8vt3I-Vm-hkhnG4rx_DUnyO7biJgHAZKKXNVTKCqgngN6IfVCdVKAIoPCIRIF1e675YTkueBjotXF5ourcdSKbHVz1xPREhDK6vp6NfDY5t7pPmpiNhG3GhTCWEEIaU06QsKb6gxfP3qvp8MatQ"}], "types": ["point_of_interest", "establishment"], "reference": "CmRRAAAA_9UAMB1CtJJZYB4hjIeeAjITeIFcFRwONNtQ4VBz5fHcqVu1ofBHoOyjH4s_EpZgM3lCPfOB_7irjhefdi2GhM5OOL3Fc2fgrxa2J1SOCLhxu5fFTzA0MfOj8_lpcmUQEhD9Dm5gU1n5eh8HI5SlODb2GhTkoUboX7BjAYfl1PXPzohQseH10w", "name": "Student Conservation Association", "rating": "NA", "id": "1c5ea7722fc0d99e9f7dfca55f5d9078224d51d3", "job_title": "Brightstar-Care---Sugar-Land%2C-Tx", "place_id": "ChIJQcqBXfDAQIYRErawO-goGj4", "address": "2990 Richmond Ave Suite #400, Houston, TX 77098, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-96.038102, 30.055621], "type": "Point"}, "properties": {"photos": [{"width": 984, "height": 985, "html_attributions": ["<a href=\"https://maps.google.com/maps/contrib/110279808588468038448/photos\">Peckerwood Garden Conservation Foundation</a>"], "photo_reference": "CoQBdwAAAMgcMbvZiDben6PKKhIexZWYoODNPYOo8ibdeVq4a3mfG6Sa3PCVpAaPQmrZBi0VoFDOtL0ZxXIhoe8dOuT6SNzzbzShgT9luSENaU4tnBZ4p9BB7yC48zzaOuiUHGx1T32DB85C1RPkWuMxg-UB08o_gu2K-588Tr9CfjM4GPpaEhBqif8gLbWRmVKhNS1FGDJLGhQnZhN6vQXeTkUCxCqWIa6V6yWXyg"}], "types": ["park", "point_of_interest", "establishment"], "reference": "CmRRAAAAq2j0A2RLHNRCGQQECOY3boayATpQosoLPlxaW19wx6jtML-K3Z3yyGGvOKbf1qtXK3tPjPfyeuaJSLTKgreo3lyw-UBFnbckYIVpdhfW6ya1AYp82GdS2iP76kwzOBrZEhDAle3eHPB69ouB9pW5mIwFGhQuPU2BGsB_sJoWG-0srJVXInlihg", "name": "Peckerwood Garden Conservation Foundation", "rating": "NA", "id": "e618a4c618cd67ce4f5fdc165f640220ab3b53b2", "job_title": "Brightstar-Care---Sugar-Land%2C-Tx", "place_id": "ChIJmUR7pvHKRoYRIIl0o73bPGE", "address": "20559 Fm 359 Rd, Pine Island, TX 77445, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.64386449999999, 29.7515036], "type": "Point"}, "properties": {"photos": [], "types": ["point_of_interest", "establishment"], "reference": "CmRRAAAADLomZiAQlBeFBJ5DFsBUX7KDbI3jGwC5uAtBlSl8fbkck9BpxR-Mf0Qk4iqYCtl_jzG6AIexCqzjARRqFBYFRgw3gzEX_48BajimqixPfMlVC1A3GAE9UfgjtGtsfFH8EhAfru6WMheRtZ6TWbNnedihGhSXvvXJ7JI3YGgiVk3LRbfaraH8EQ", "name": "H2O Conservation Technology", "rating": "NA", "id": "30c07988ef8dfc62dac712b9d587daa4a36f2539", "job_title": "Brightstar-Care---Sugar-Land%2C-Tx", "place_id": "ChIJIWZRKeHKQIYRXxta3wOMGGc", "address": "1725 Hwy 6, Houston, TX 77077, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.5705632, 29.7714443], "type": "Point"}, "properties": {"photos": [{"width": 3024, "height": 4032, "html_attributions": ["<a href=\"https://maps.google.com/maps/contrib/108143329814504597326/photos\">State from Jake farm</a>"], "photo_reference": "CoQBdwAAAO08oPQg7F3X90XG0GmWd3Kh9z8hFo0ytBmShwJW3qUyeWEfbKiTsmYjHtcH-4YKnVE8TA-WOBXPCHEdErZHtCg3FLVf4oWLoGyYLh8b3yLQzp8JSTx2k2l0rP9NqiHWl3y6ft13WpErVLhZcX1uU6hyQpwxn5EoUzA29PTYC3Q_EhDwHXnqjFSIWpU6Zzlx0hFbGhQj6bjO_B67eac-nxqTEZCGG7HHFQ"}], "types": ["park", "point_of_interest", "establishment"], "reference": "CmRSAAAAyMdwb6LdNKHl_uTAuvmWPXc3BPCSQ5ClbQzBILoVedpNu12ROTEZFsKhAHeYx370ooHCRli0TnoYuYsY74jlP11JPiZn5kTiLbOVxEd14cr3AOyvEHrwq2IXrIzJCZgtEhApLK1t_NxquvBfqgEq7arnGhQfNwYNMx4AHUaSNCSLHgEWnPb6YQ", "name": "Houston Audubon Society", "rating": 5, "id": "050a5458d86bdd1cee7b09678bd6256d0a20a73e", "job_title": "Brightstar-Care---Sugar-Land%2C-Tx", "place_id": "ChIJlQOxwVDbQIYR2uX_TZl0TYc", "address": "440 Wilchester Blvd, Houston, TX 77079, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.56820189999999, 29.770778], "type": "Point"}, "properties": {"photos": [{"width": 1800, "height": 1200, "html_attributions": ["<a href=\"https://maps.google.com/maps/contrib/108765250995932379967/photos\">Audubon Docent Guild</a>"], "photo_reference": "CoQBdwAAAO3phYVx6AdI4tEN2EaONUN-y8olrdkWhccoptYFqlSaSEMIJyr6gGIbov4qk8A9zE0S4c7JoNZtKYGcx1bvk13yqEy4oxACRk8mJoojMyZuXquM3fP_TtPaLDmFCDaEVV1EVoFCI-twrQNNC-9vi9Z3-Sa8v9qQ1OvzIDMtOlX2EhB8rC6AFv7hyzF6lnTYuZxXGhTD7Q225fDLiyGiNSNEx7IQsW2New"}], "types": ["park", "point_of_interest", "establishment"], "reference": "CmRSAAAAoip7GukaSwv91kUPHZVbR0SSUmESWjn0INg9LHjJSOpWV0Ud-_UMWgsURjCBmJ1vlQz9jaux1nOmAD3Sf8zQOF8H3NgEduJWg9Ll--CbRcujUarJ3t2Kc_mahMKFd8J_EhC4yPv92XLoVTg1BCTZlnapGhRAWlrv57N-U3KCMsaFVTE9k_WTJg", "name": "Audubon Docent Guild", "rating": 5, "id": "7ddd5daf76cc4979e2ba6b062322d1c77d5d1c07", "job_title": "Brightstar-Care---Sugar-Land%2C-Tx", "place_id": "ChIJI9XyNFHbQIYRtwHb8EtTpeU", "address": "440 Wilchester Blvd, Houston, TX 77079, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.44932349999999, 29.7803218], "type": "Point"}, "properties": {"photos": [], "types": ["point_of_interest", "establishment"], "reference": "CmRSAAAA2pcHOEHZ71QUUlJmEep3F3nwElQoLG0AKHunN8UxqLc3zAj9fEhAvNhNncyWplxSwytGLhAAQXEP7b6EkqGQrzubde9hMitTAaG2aLQXwsFdiCTBiuWA3IKwOFWCSHhsEhB5mi_U0--6ezidV9IVsn5VGhRAa7tqpVxmMj2DY5Kvf7wswsYSEQ", "name": "Coastal Conservation Association-Tx", "rating": 3, "id": "7258b034e119f31e82320bca6e72781ee9f79d75", "job_title": "Argus-Media", "place_id": "ChIJcekacM_GQIYRPzL13cgQrPk", "address": "6919 Portwest Dr #100, Houston, TX 77024, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.47039, 29.655454], "type": "Point"}, "properties": {"photos": [{"width": 5312, "height": 2988, "html_attributions": ["<a href=\"https://maps.google.com/maps/contrib/101184977609161362375/photos\">aug4</a>"], "photo_reference": "CoQBdwAAAD6bCjrSGDLkRPcI3LgjEIuaefIlaZjv_S5sD8oOZkGP8KpfF78UIPzfmFyXgsZ30bji3KSWwjiZb3F9gGDMdgX-JoBLtOmfD4IAED4DHshzqXVDbMvKLjyHyPFWdHHgpy_9EcIaQRARlstmx8xDL3nR2ZZDl-rOs27Iv7F1IcWcEhDZlbiv6iMpJNkYt2qgHlu6GhQTBwa2nW3QoRZkdLO4EjnspW4EqQ"}], "types": ["park", "point_of_interest", "establishment"], "reference": "CmRRAAAAIvoRMwJajQOvHIjZl_-ckZMIt4AKreft-0eNAMv-1Bdy7v1v08zFK1sA-1Nbgb_h_B71agxzaDuXKpOL9cy_OD0sz_efp6pqlQXYNR0V_9RdiXS7lvVZkpSiJVgjtufSEhCzuzvnDh7C1ikosYXTrhAYGhQ32UHhTf8gSx2mp3Iu8U0KKdSycw", "name": "Willow Waterhole Greenspace", "rating": 4.3, "id": "0127506e8071350c2d48f0ca56e939045297a0f4", "job_title": "Argus-Media", "place_id": "ChIJR6_2zTzqQIYRsA7wExgfDWs", "address": "S Willow Dr, Houston, TX 77035, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.4003322, 29.7388505], "type": "Point"}, "properties": {"photos": [{"width": 1136, "height": 640, "html_attributions": ["<a href=\"https://maps.google.com/maps/contrib/117056878997299689379/photos\">Marisol Brown</a>"], "photo_reference": "CoQBdwAAAL_NcvAatKGkTXZvT4DtStF1T6qm9ZQ1Iaw_wntd0YevANrRPlp3_ibyrecHoaSrMAYeMgrxhQovqJQ8JCwZZQZplkKMuZCfYFvpRNeJtNYbxeW8DpQ28axkAUb0lDh_yLK5FaFVF2A5Ow0eTlauWXLnxdfnWwyCRYT9FILzLoXjEhC9D6fZgRfVXdPF_6KWO7c7GhTjd1Kc63yEQS_hyuFtOC4OtlVTwQ"}], "types": ["point_of_interest", "establishment"], "reference": "CmRRAAAAewl0aDS8Ui9RQEfzKA-kVCcoosbEiBnPruyzRzV7JPBiZAx5XhR3TH_t3COCGjgEnwgSBCHAepQL034JC72zjJiYziGNoR_dYfDi8aYW3JjWO5WgNn7AZX-WYnBS6D7cEhBmYpex4HXWVxvqcMvBzmpZGhRARhGnNfSrt_PDQKvDqbHspEscog", "name": "Masters Fine Art Conservation", "rating": 5, "id": "a462c2eef4e22ea319485ae7b84f3d20756cbdd1", "job_title": "Argus-Media", "place_id": "ChIJp8u2bZvAQIYRbosnWz6cVmY", "address": "1612 W Alabama St, Houston, TX 77006, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.3876169, 29.794149], "type": "Point"}, "properties": {"photos": [], "types": ["art_gallery", "point_of_interest", "establishment"], "reference": "CmRRAAAA-ugbVsnazo4wKtKla7BwJkrDld0lw-DgGH_v-aR5HoW1hZZNxJN29YSYGjuQNt1aInyHsmzUB7qjNd4-j8vDKYvWx_SL5zqdgbBxw5lK3fDRYoJRd4sKHXwwKA7tag9NEhA6jMiQVBvWsS3ptmyNJMmUGhR3FAbsKywVSNE_kvWZhPXi0qZ8fQ", "name": "Whitten & Proctor Fine Art Conservation", "rating": "NA", "id": "883a8c5ef35ab28e1630235ad65a6b16506a67fa", "job_title": "Argus-Media", "place_id": "ChIJ8YuXE6K4QIYRn1SF1hazFEw", "address": "1236 Studewood St, Houston, TX 77008, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.3858767, 29.7300997], "type": "Point"}, "properties": {"photos": [], "types": ["point_of_interest", "establishment"], "reference": "CmRSAAAALLBzWSaaCxP1N8HorGBOScDbeIl5deST_cTcuO0J11AFqjlQpR6vrHBh9Rl_cKY2SkZAaX8bv4M-9G9MbJOusVxwxbB44-L_M4XxCli5lT6q1MuraAoHMZ49oqud6G_PEhB9Hy2G-GGdKbX_nRJ7JgqUGhQF_6SS4z0MEuutgJDv_-wqR1sDTA", "name": "St Mark Fine Arts Conservation", "rating": 5, "id": "ea2d4bac6d74716b33f456dff3aae0cc0b43cca3", "job_title": "Argus-Media", "place_id": "ChIJKbDEoXm_QIYRcRFBlp0dE8A", "address": "4901 Main St, Houston, TX 77002, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.483218, 29.7482286], "type": "Point"}, "properties": {"photos": [], "types": ["point_of_interest", "establishment"], "reference": "CmRRAAAAyA3TfLJ5jr8Wi7mJlzsF-TwbBo1N4w7B5LxcpnJ5G5s0pWy918x-aHqXH9_iG4uAvRLlBRKmXYA4D1wsWZVoEzJtO5spcuHwG3M_A0PfAJr2dNgFXjPFTRGnuHiyvCMMEhBb0l0ehfAXB3pNe-KHgQrAGhQNCHO9TOGa_N3_R7oohZqZ2HAMvQ", "name": "The Nature Conservancy", "rating": "NA", "id": "90af6fb9fb926dde9f7103577cebc4150bbb1dec", "job_title": "Argus-Media", "place_id": "ChIJq-m4EX3AQIYRJkn4Lhccp2E", "address": "1800 Augusta Dr #240, Houston, TX 77057, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.42318089999999, 29.7345943], "type": "Point"}, "properties": {"photos": [{"width": 750, "height": 437, "html_attributions": ["<a href=\"https://maps.google.com/maps/contrib/106788706324997826205/photos\">Erika</a>"], "photo_reference": "CoQBdwAAALyOHz767Kzy3qR-mMCV3CKmoeHWea7PV3BBZARiQQgvfRsChhxiMYiLiTzcq497x8Kb4bjINFiJIGSnSV_P8w7KKLk5gDMJ_PlAsya5Rel4chtLr4FGlEVhQIbXBww02B-5euxwOCSQ7oxIvPHbSJxpjmRc5dkythCRx3FEogVNEhAzbzerToNeXQZmLK9rj0E0GhRPokSsOLkuVLte6-voxQ3paqdphg"}], "types": ["point_of_interest", "establishment"], "reference": "CmRRAAAAARIK5FFjRjsRifVGJQ-FSpeRhIiwdOLr79Lh_tfRP5BzG3qluBbQ8GBtfBF0nrVXCjD7Kmz5WsHVkGczT4-2Umv7mEaa4Jz1VOt4M4JDr9qur7KZkJJHtKzLNWYUKEqCEhBQN-KIcHLPrBPTzLoZYNlOGhQkOmitPQR5oj_TssxtoqG3Cm8aNg", "name": "Student Conservation Association", "rating": "NA", "id": "1c5ea7722fc0d99e9f7dfca55f5d9078224d51d3", "job_title": "Argus-Media", "place_id": "ChIJQcqBXfDAQIYRErawO-goGj4", "address": "2990 Richmond Ave Suite #400, Houston, TX 77098, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-96.038102, 30.055621], "type": "Point"}, "properties": {"photos": [{"width": 984, "height": 985, "html_attributions": ["<a href=\"https://maps.google.com/maps/contrib/110279808588468038448/photos\">Peckerwood Garden Conservation Foundation</a>"], "photo_reference": "CoQBdwAAAFGB_QGMn_Kt8E_IMP9BABhuBmlQYqAkLvti-03SFbfg_EWKOtdKLitWU3yDr_cfELOGUrn_YGxAjGoWKUgh6iCVUSFlyn1T9qmx_M-l-gf1tEwrf5vSrwPDMa3NskHiQaJgJZkbz6X0T6PyoQt0UxK3uXVr1d9Zk3nuO_PFg1K-EhAX52lF6cP3PrjFmlb_ZmXkGhSBe__FxOuvzz-vQtM3HJ37A8zX3g"}], "types": ["park", "point_of_interest", "establishment"], "reference": "CmRRAAAAY4wnFe4oPIBkKY79i0H2PkJRAqxbsY9pHurt4aVW0F56v1pduXiKQQ5kdfqcCpy56lYk4n9CpDfuhFEI1HP6RECIAs6pI4f4N6hM0ok10iMPJ4VtUZJbivv_Ovtft3-REhCHwaunD9iILRA1RPib8QOUGhTODg84KoDXHu2c7MOzjCvAA5aanw", "name": "Peckerwood Garden Conservation Foundation", "rating": "NA", "id": "e618a4c618cd67ce4f5fdc165f640220ab3b53b2", "job_title": "Argus-Media", "place_id": "ChIJmUR7pvHKRoYRIIl0o73bPGE", "address": "20559 Fm 359 Rd, Pine Island, TX 77445, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.64386449999999, 29.7515036], "type": "Point"}, "properties": {"photos": [], "types": ["point_of_interest", "establishment"], "reference": "CmRRAAAA1dVZNUhT8s9Rv67gMqzCBkyLa9m7fbINd4sOf0A0DfKABaAG-XMPMEWC6yqLxXbNgdQ76v_6Ow_1R9bS6XSDPuBs4QvyoJwlxMS4EXONDh1LxQda7NtBICc3UzuWE73QEhCQBRz5ZiV4Y3DnvF2Tao1DGhRj4CdWcU9ZuA65HtMAjV815yFqVw", "name": "H2O Conservation Technology", "rating": "NA", "id": "30c07988ef8dfc62dac712b9d587daa4a36f2539", "job_title": "Argus-Media", "place_id": "ChIJIWZRKeHKQIYRXxta3wOMGGc", "address": "1725 Hwy 6, Houston, TX 77077, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.5705632, 29.7714443], "type": "Point"}, "properties": {"photos": [{"width": 3024, "height": 4032, "html_attributions": ["<a href=\"https://maps.google.com/maps/contrib/108143329814504597326/photos\">State from Jake farm</a>"], "photo_reference": "CoQBdwAAAFYIZQFkqm8uB1-iz8Hod0eeJo5yFZ0jhqhsmJhEPL04wto0hbMNS0WWSp_eZSVKoWC3sFOvWYhnnVp3fbPYU7KUK2EnWBkKYlp8MD5e2yfzgDbSy6oqQIpabqcn9N-QfCEt5CICG1Ywj7KqXEessU3-oIk197RKffQB4qu3toHGEhAf5i7mcGXeYEZ35kU4PQTrGhTcBnEdVB0z11ly9n9ZNX3enekNLQ"}], "types": ["park", "point_of_interest", "establishment"], "reference": "CmRSAAAA5cM9HRH7Ak9h7ZY5zFxVnWozlLqZJpb9ThqILHRP5z5OqZ7c10zCGeBn-6zwE0AigA8sjLSXY1teVe9XbAlnqsnypKT5aCT4fqxembd2wEO9usXelGfKS32llHad7W3pEhCWPPDE7-ntPEyBRpyqoC4-GhSm9cBsthmXTjKN-vYPTmRHBEKdxQ", "name": "Houston Audubon Society", "rating": 5, "id": "050a5458d86bdd1cee7b09678bd6256d0a20a73e", "job_title": "Argus-Media", "place_id": "ChIJlQOxwVDbQIYR2uX_TZl0TYc", "address": "440 Wilchester Blvd, Houston, TX 77079, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.56820189999999, 29.770778], "type": "Point"}, "properties": {"photos": [{"width": 1800, "height": 1200, "html_attributions": ["<a href=\"https://maps.google.com/maps/contrib/108765250995932379967/photos\">Audubon Docent Guild</a>"], "photo_reference": "CoQBdwAAAIZ8UlFjUOO44Cjchunu74g3Mvu2Y_QXGIMQMsgc7xLGgBvOLkiwRnFr4F-zNStigt_lBifS7LCH6w0z62yuFkIt7MxMHSb2M0Y3H25MeM_qB03GxGtgx_KQdGHKCO2zvcZgyaEl2iKY3HAm6uEA7geyOabnNymipZVGe6upLB3fEhDdPV3fTUJf0dAgRhktAvrKGhTZVal_usAHKUxgTi03fVAqueJ6Ww"}], "types": ["park", "point_of_interest", "establishment"], "reference": "CmRSAAAAC1MNclWxZFoShuCCKZIw6s4dYIuabOrLeghG-bayoga35dw-hLX0bvCQwcyhEVfEuEMGpO1ohHOI2atHP3itBHfdYDOPUTJINYB_YqEhJoB9Ltd-L1KL7GaVoY3z7Pw0EhBMcNyGM_-tiJ4_8KzaKq3MGhQy_teBwePIY8Q33QuN155z_WrQrw", "name": "Audubon Docent Guild", "rating": 5, "id": "7ddd5daf76cc4979e2ba6b062322d1c77d5d1c07", "job_title": "Argus-Media", "place_id": "ChIJI9XyNFHbQIYRtwHb8EtTpeU", "address": "440 Wilchester Blvd, Houston, TX 77079, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.44932349999999, 29.7803218], "type": "Point"}, "properties": {"photos": [], "types": ["point_of_interest", "establishment"], "reference": "CmRSAAAAuS_ADFHwFIYobC3uwnEmAY6xUMct7fZNBhD7VwjDOjv4Be_zAeV0NWPkG_15lJnEit9W2jLEeHKiQ8BisbXN2mkL8FaTizV-Nf6SGYq0Jcg1tWRH44Agb2eh7M6aKaEyEhBVjEDksjqNizv4nCYHv6HgGhRPwm3ZrB6mRrjGXOV-46EzKLOWQw", "name": "Coastal Conservation Association-Tx", "rating": 3, "id": "7258b034e119f31e82320bca6e72781ee9f79d75", "job_title": "St.-Joseph-Medical-Center", "place_id": "ChIJcekacM_GQIYRPzL13cgQrPk", "address": "6919 Portwest Dr #100, Houston, TX 77024, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.47039, 29.655454], "type": "Point"}, "properties": {"photos": [{"width": 5312, "height": 2988, "html_attributions": ["<a href=\"https://maps.google.com/maps/contrib/101184977609161362375/photos\">aug4</a>"], "photo_reference": "CoQBdwAAAIAJ0xhwKVlV1WD4HcNJJcMvC3og5oLe2UBI15Pt2-O1FqlRBxzqFVnOwa6YTAeFb4ennIJURWLFBk8yaRj283w9ZenJ6AoE1WlKFC8ugMXzS91-32An25_dfY-_z4rzjP6xp6esJrYL4SmPDZTiwKIY085Zk74WuPW483mawzkOEhCDczX39f4qCDRUmNUTP1GPGhTKkAFh84wGafFQydXkZF3BvLZQBw"}], "types": ["park", "point_of_interest", "establishment"], "reference": "CmRRAAAA-EKDdUN2ZfROEJYY0tzSNZex1OearM-PDK8AjTkBYvBiJmbjXidh39JHpNkj0Zy90m90nUqCU0lUCowWKsDwmBpnwusvcpfv6rSVE5M4Gr5ohFaStUXA99KU7-FBd7_uEhDTyVIrt1WyLdw4ip6u6vC3GhR3onZw9t7jPX3LgNd1i66gVMDRsA", "name": "Willow Waterhole Greenspace", "rating": 4.3, "id": "0127506e8071350c2d48f0ca56e939045297a0f4", "job_title": "St.-Joseph-Medical-Center", "place_id": "ChIJR6_2zTzqQIYRsA7wExgfDWs", "address": "S Willow Dr, Houston, TX 77035, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.4003322, 29.7388505], "type": "Point"}, "properties": {"photos": [{"width": 1136, "height": 640, "html_attributions": ["<a href=\"https://maps.google.com/maps/contrib/117056878997299689379/photos\">Marisol Brown</a>"], "photo_reference": "CoQBdwAAACUPNIwsQcPJRywNS51PAl8aW9mXKwhDaoapC7RQp322R9S7CfmgDdr-QrXFzCv7KGMUDA-1WWuaGJWjtKMzk1wU7tb2M9J6AbRX4XA5Ylgo2TnsxTVfjka1oSQMIjncbDLakYu311NmjYkJvoG1iY1EhaOt0ZXKpqzjrH67ZYhwEhBVw_9v5roDFCmF26K7KRogGhQZOxIEaoSreRA3uul2ANh56Z8HyA"}], "types": ["point_of_interest", "establishment"], "reference": "CmRRAAAAvxbuxQhzbkJ4Ezb44BOWPTa2FO568CdMVlBHWYo531WDzuY0xgHc8GXboCjy9FGj6kMwtGBzbSk28wSlTcajcgKMjLDYHcthUFMj4sWSOYysdzCmmDyDmsiBU1BG-cg0EhCCFevZcCtdEYgrCGryFiT8GhRowJe3zI7WLIXlQGsxgc0JxhSlUQ", "name": "Masters Fine Art Conservation", "rating": 5, "id": "a462c2eef4e22ea319485ae7b84f3d20756cbdd1", "job_title": "St.-Joseph-Medical-Center", "place_id": "ChIJp8u2bZvAQIYRbosnWz6cVmY", "address": "1612 W Alabama St, Houston, TX 77006, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.3876169, 29.794149], "type": "Point"}, "properties": {"photos": [], "types": ["art_gallery", "point_of_interest", "establishment"], "reference": "CmRRAAAAtTI3MSBvlJR-JOmSWZumr9DEy46RN-jl7BjkXhXQKjWG27c_Zo3roaFYfdEge-t5RbQv8yPIlYUE0TCqk3CpGVOaK5F6oX1PlDVCVh_BHw1I03gjRIcEwECPNtQ-N8PpEhDcAuoMbuMjBdqknW5FATFOGhQqGziPBcuZ7EZbU2O06vDTB4yYaQ", "name": "Whitten & Proctor Fine Art Conservation", "rating": "NA", "id": "883a8c5ef35ab28e1630235ad65a6b16506a67fa", "job_title": "St.-Joseph-Medical-Center", "place_id": "ChIJ8YuXE6K4QIYRn1SF1hazFEw", "address": "1236 Studewood St, Houston, TX 77008, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.3858767, 29.7300997], "type": "Point"}, "properties": {"photos": [], "types": ["point_of_interest", "establishment"], "reference": "CmRSAAAAfsgwEUHOv-7DHEQgHpn6-IJtDoxLt-x1klSjbcFincKi6T73s9AfookkaIGhzWz6f4sX_8RNN-hD2VxXHeENntecOSgPNKqW09T5XQ1PuhPLlCSByT4UDoZwdg5k6r9qEhCHHtZW9kZ3rebAMcR2DLAoGhRjeF1rZ8lb149zlDEJjopXiBVWyA", "name": "St Mark Fine Arts Conservation", "rating": 5, "id": "ea2d4bac6d74716b33f456dff3aae0cc0b43cca3", "job_title": "St.-Joseph-Medical-Center", "place_id": "ChIJKbDEoXm_QIYRcRFBlp0dE8A", "address": "4901 Main St, Houston, TX 77002, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.483218, 29.7482286], "type": "Point"}, "properties": {"photos": [], "types": ["point_of_interest", "establishment"], "reference": "CmRRAAAA2bMInAc5f_AppIZaMLXT335kvbIBU2_E3-TtZs_NYEjHk8PcCRvXF4CR_N_ux3UQEPWZ2PXoXyfoVstMP1zH6jZ1ka5NSkMfOIGnjsarNaciim3jRVKTJmMSWZ3eTEO4EhC2m9B1xoGw8Gi9nzCLEgE9GhQpDU5B_bV4BwHpALrDxG1P2JcYbQ", "name": "The Nature Conservancy", "rating": "NA", "id": "90af6fb9fb926dde9f7103577cebc4150bbb1dec", "job_title": "St.-Joseph-Medical-Center", "place_id": "ChIJq-m4EX3AQIYRJkn4Lhccp2E", "address": "1800 Augusta Dr #240, Houston, TX 77057, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.42318089999999, 29.7345943], "type": "Point"}, "properties": {"photos": [{"width": 750, "height": 437, "html_attributions": ["<a href=\"https://maps.google.com/maps/contrib/106788706324997826205/photos\">Erika</a>"], "photo_reference": "CoQBdwAAAOvg_NDSa3X8n_TsPc2oRtiAg7z4oEekj32V75G5GdVmC6irFkfd8qV16yRKTYaedCwcP1sM8aGMkI_o1702LOz-i_GdsNisK84mdPtrvHTCm-n81lWZRxEdo5iU5Fh0WSaJCXaDf_44MARKxdAZjEVAfNgnnFJei5rp3Omjix-2EhA4EfthB2TOmv0soScXKwPAGhRpQThFi4kGwSlMbUVANUbPsXxFGg"}], "types": ["point_of_interest", "establishment"], "reference": "CmRRAAAAsDKHVPXNOiGKuDMWMqAFJnYXCaXY2F2yJmz8iGu85xDld_pbXvqkpN_no9ZMQ1SaQZXjcQocMTGgmGgZ_7We5jbHfR4gHAx6Ynjm547Mvs2A60d_--g8yLZBlnX6WgOdEhAzefQ4O8jslUfG2B9Sjj6AGhQckWrR1CRgUZo-0Ar2EyiIasmkTA", "name": "Student Conservation Association", "rating": "NA", "id": "1c5ea7722fc0d99e9f7dfca55f5d9078224d51d3", "job_title": "St.-Joseph-Medical-Center", "place_id": "ChIJQcqBXfDAQIYRErawO-goGj4", "address": "2990 Richmond Ave Suite #400, Houston, TX 77098, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-96.038102, 30.055621], "type": "Point"}, "properties": {"photos": [{"width": 984, "height": 985, "html_attributions": ["<a href=\"https://maps.google.com/maps/contrib/110279808588468038448/photos\">Peckerwood Garden Conservation Foundation</a>"], "photo_reference": "CoQBdwAAAJMHCtGtmi9fOgdknveWXUGcGGft-iTOECZpRgN-c-vgpBTQWexkYdjrDsNXDhsSGQsgmXrSem6axWf3rdTNjyar6yitF0RFLek7yil8DFQscfc1Y48nxhcyra5DYBnF500G6AaGfsqFG8JIU1FHk3CZFWvfPpuxkZBsGazfuC-oEhBVRq1RacIMQibnXeDukH6wGhS3xczQBftrhfJBtrDSTyUlgSezTQ"}], "types": ["park", "point_of_interest", "establishment"], "reference": "CmRRAAAAZJhRnqz1PcRPMe7Nhpy7wD4qDSq6UjHr1vf-bpVpCQ2SJjC84NeI4wTa7CbqT0gRXNaLsENEpHK5DraY58HQjLqlIXmmFm2rFh6FmqkJ0stWrexX-QZ3Q2PsiOWaXQuXEhDECJKLgm06n7LQ5E_MNvKwGhTRmDzaU4ZMhvSkF7zJxBE1mxyt8w", "name": "Peckerwood Garden Conservation Foundation", "rating": "NA", "id": "e618a4c618cd67ce4f5fdc165f640220ab3b53b2", "job_title": "St.-Joseph-Medical-Center", "place_id": "ChIJmUR7pvHKRoYRIIl0o73bPGE", "address": "20559 Fm 359 Rd, Pine Island, TX 77445, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.64386449999999, 29.7515036], "type": "Point"}, "properties": {"photos": [], "types": ["point_of_interest", "establishment"], "reference": "CmRRAAAA41Wcw6IV46ir1R1LxQxH4BvVAhx9ndU2dqbfRqEsW4oCOIfbikTwLzrI0LaV_-XrqWYLAxUc3VIoM3vLFQf28lyeqoj0JZ4OVobIxEKGmZK4yri72pn73SUvM5WdN-eWEhAYgjPQaJ-CQQNFJxro2ds1GhSdEt2qBcZleHbJHw41s3RsfpU3-A", "name": "H2O Conservation Technology", "rating": "NA", "id": "30c07988ef8dfc62dac712b9d587daa4a36f2539", "job_title": "St.-Joseph-Medical-Center", "place_id": "ChIJIWZRKeHKQIYRXxta3wOMGGc", "address": "1725 Hwy 6, Houston, TX 77077, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.5705632, 29.7714443], "type": "Point"}, "properties": {"photos": [{"width": 3024, "height": 4032, "html_attributions": ["<a href=\"https://maps.google.com/maps/contrib/108143329814504597326/photos\">State from Jake farm</a>"], "photo_reference": "CoQBdwAAAAKI2NdToMD7D0Daf8lHbOMcY65I2-w-i0yACIPNhexqroPOtDGriTBnqu6X5K4rtRApmO8Nlm8jgkYTALUWpRC_t3cGvVZf0U_za6qeI6etkoEjas0WKWqLjflabll7kP17i0TyyLfDrmNb4neXILoREOn5DtS61MjyGPSAbDEzEhASuAfH9BHhOdtg7e0x7008GhSSuo0dGqiaGhXCClQ_Hxrdjt1ZNA"}], "types": ["park", "point_of_interest", "establishment"], "reference": "CmRSAAAAB7c9ysHf_8ch1CRYyLYVxNGu8pIyKt1vGXlN7Lmjq3Crerq-VKYfFj8IIdXXDjWmKjv6wXwS9XgkomgkCWf2N_moXXpOo72BI4CpAEOJQ9bsqRoFdG_eLfR8dZAkcBDfEhC0gUDxmW3SxvYbZfcyLAPVGhS5DYR1xkrApfQS6QTbTdWshneb8g", "name": "Houston Audubon Society", "rating": 5, "id": "050a5458d86bdd1cee7b09678bd6256d0a20a73e", "job_title": "St.-Joseph-Medical-Center", "place_id": "ChIJlQOxwVDbQIYR2uX_TZl0TYc", "address": "440 Wilchester Blvd, Houston, TX 77079, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.56820189999999, 29.770778], "type": "Point"}, "properties": {"photos": [{"width": 1800, "height": 1200, "html_attributions": ["<a href=\"https://maps.google.com/maps/contrib/108765250995932379967/photos\">Audubon Docent Guild</a>"], "photo_reference": "CoQBdwAAACTwd7fkxrVhk4P382PJ-mJ3H9h0beaSp4aZP5dRBLuTNjfT6xFpbNHh7o5YcYpp3m6qxvNivgd3JZqAgro5RGXlwKsxgF7m1l9eOE2BXH1tM_sk110YBmwwqGhKqyZlMqZunMF7A_AhrXze0O3SMxShJ-3vpMBIKzhY64oa5VaXEhBCip4hEoS8fd1FcSEXVIngGhRk0a31Jg_g-E4eXRbl64nZcCwWiQ"}], "types": ["park", "point_of_interest", "establishment"], "reference": "CmRSAAAAGaFe3eo9CNJaUkx4CFne8rygeCYzqJBWS3GUOpHPejKbykwOShioY67fP0iHA5xaec_Miv_kLtybKgnGXn9_bxMoQW-792duRBpVSYTB6D5EUXD6S9-FM61cbWYu_wENEhAI4ruZ4ivi7Wax4iqJAmIeGhRyIKTfqXHp9-Ep7AaGTowOSKgN-Q", "name": "Audubon Docent Guild", "rating": 5, "id": "7ddd5daf76cc4979e2ba6b062322d1c77d5d1c07", "job_title": "St.-Joseph-Medical-Center", "place_id": "ChIJI9XyNFHbQIYRtwHb8EtTpeU", "address": "440 Wilchester Blvd, Houston, TX 77079, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.44932349999999, 29.7803218], "type": "Point"}, "properties": {"photos": [], "types": ["point_of_interest", "establishment"], "reference": "CmRSAAAAyDe16CtNZcSz3GK1LskTQeZE87ydEjGEUaz2fHFL6CZceMuMjSg-y4A2jYQ2jiqu3p5BWFyrnaS0ia259BVqzEO5GQCePmRobVXMonlae2M15Kw2gibXiSJFhOD5KNE9EhB5FjEF0hZW9n-wTmyV25aFGhSyUVV3g-GzabxMP34eAaENYsBqnQ", "name": "Coastal Conservation Association-Tx", "rating": 3, "id": "7258b034e119f31e82320bca6e72781ee9f79d75", "job_title": "Trinity-Consultants,-Inc.", "place_id": "ChIJcekacM_GQIYRPzL13cgQrPk", "address": "6919 Portwest Dr #100, Houston, TX 77024, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.47039, 29.655454], "type": "Point"}, "properties": {"photos": [{"width": 5312, "height": 2988, "html_attributions": ["<a href=\"https://maps.google.com/maps/contrib/101184977609161362375/photos\">aug4</a>"], "photo_reference": "CoQBdwAAAJ6V90QThGTafpDM1NSOuYiim9Qr3LH5JrcO3r7ekCInSh0cvv6vgNS4u2WdFtbAQknYXI3s_QfR2KSOqoKrvMUV2XjJXnUR3n606uQi6s3qdYhbVbldbVS3WwIat7Wi0wGF2oFwGh09OXcxIU5hdyrlPHnc2YUW5U3n1bJ7pZEQEhB5rPQoTFe4I3G2cAbXOse3GhSpiMnIo1LGnUq_j40NXvrjaJdzCQ"}], "types": ["park", "point_of_interest", "establishment"], "reference": "CmRRAAAAO0C3qkYMWIPZluzxjdgSiqSQCY8M5bJgUElHuDdO2k_1tcJ6BMr-h5_NGStIjlOghseYIE8CfLJuPeCxVEBLabLbTZO_ql8zsK_2vem5suSJ_YBqZuvxyrOfiCjbsS5FEhAR7ThIao0qsolrImwZ_X3kGhRkOobOFBZIiu7Vkuaf0THlys9T0g", "name": "Willow Waterhole Greenspace", "rating": 4.3, "id": "0127506e8071350c2d48f0ca56e939045297a0f4", "job_title": "Trinity-Consultants,-Inc.", "place_id": "ChIJR6_2zTzqQIYRsA7wExgfDWs", "address": "S Willow Dr, Houston, TX 77035, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.4003322, 29.7388505], "type": "Point"}, "properties": {"photos": [{"width": 1136, "height": 640, "html_attributions": ["<a href=\"https://maps.google.com/maps/contrib/117056878997299689379/photos\">Marisol Brown</a>"], "photo_reference": "CoQBdwAAABMepfCv5XHeA-KTAM5GrEoHCVDR9bjVZTgFbjcYfRuWNFWwn63Dj7aGlZ3Tqvgyo2cfOIDQqJEfWkv1FfG4Im0OcZZUmUMX4qZdZ1-WfvU7d_8BYrA23jlwDZRIL1SaePOYsPnHu4t6uYYyXrsw4iVeqbvretqrpoMedpfTVU21EhDdbz9UH7rDy6zDhtkbf-quGhQoBI_y4rI5IBZQSgQ4wYHw4mTamQ"}], "types": ["point_of_interest", "establishment"], "reference": "CmRRAAAAt6SZu4_EuHxJx3zr-5QbK8dcX5Y-2U2EFKtWBtU3eBEEqMi1zaDZEwU9cCl7s5SrvPOHMAf611z50quI8YAueRTWLvhB-OqvSszpCT08G8TNpCX3rDrdDHiPNV3-b9krEhBCabX3yu7fAbQTOJHeD0ssGhRRoDN1x3JSQNItzX0oFNwiWy8PpA", "name": "Masters Fine Art Conservation", "rating": 5, "id": "a462c2eef4e22ea319485ae7b84f3d20756cbdd1", "job_title": "Trinity-Consultants,-Inc.", "place_id": "ChIJp8u2bZvAQIYRbosnWz6cVmY", "address": "1612 W Alabama St, Houston, TX 77006, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.3876169, 29.794149], "type": "Point"}, "properties": {"photos": [], "types": ["art_gallery", "point_of_interest", "establishment"], "reference": "CmRRAAAAAbyXUJEE7yIhDtM-8vb5Zsv8RZzMsZbF_J0FwmzqCVKAqQxRG0PF_rNw_-4NgKXfLacptIXhLIo7vb4tpKUwrzGgh48rBsi0ciGYaEBsPp3Bg8pFO3aK1w_AOQYRfyZ6EhBngUX3RORxYTwUmIY_COZOGhTyn1_WI_eRvMA5EqgxOs8GP73dfw", "name": "Whitten & Proctor Fine Art Conservation", "rating": "NA", "id": "883a8c5ef35ab28e1630235ad65a6b16506a67fa", "job_title": "Trinity-Consultants,-Inc.", "place_id": "ChIJ8YuXE6K4QIYRn1SF1hazFEw", "address": "1236 Studewood St, Houston, TX 77008, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.3858767, 29.7300997], "type": "Point"}, "properties": {"photos": [], "types": ["point_of_interest", "establishment"], "reference": "CmRSAAAAm5lPN_TGxF7wIJElQvZN17S-Kl7qpz_yAjs5iOk4a50UHTjC6_F0dm8f0pEoYgt5uDvXQwSXR6bDMZ_9R2sC46hx-We6s8VIyGrpA2uaMi-hQStU7ApFNjZTsAdTNDJ-EhAFl7x0Q1B8rIuuHmFVG3E8GhSYfnqAOd1J7tK_0H7JjAuq6hhbYQ", "name": "St Mark Fine Arts Conservation", "rating": 5, "id": "ea2d4bac6d74716b33f456dff3aae0cc0b43cca3", "job_title": "Trinity-Consultants,-Inc.", "place_id": "ChIJKbDEoXm_QIYRcRFBlp0dE8A", "address": "4901 Main St, Houston, TX 77002, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.483218, 29.7482286], "type": "Point"}, "properties": {"photos": [], "types": ["point_of_interest", "establishment"], "reference": "CmRRAAAAU60nUVI-b-OT4upRm_fcAF5nfNlAuo3zD8PnO8C4NM5rO4w_u5CFg1BnNC-1pvw_G0nUCgl6hHHSGkBvepc452eyoAskhrWiP8y_BaqT6ugpDK2Sk3496HUs7wePTq8-EhCfzjZC_GVgLIpT9k5k8eHSGhScV8QtAOFMIKFirdp0Href99Iz7w", "name": "The Nature Conservancy", "rating": "NA", "id": "90af6fb9fb926dde9f7103577cebc4150bbb1dec", "job_title": "Trinity-Consultants,-Inc.", "place_id": "ChIJq-m4EX3AQIYRJkn4Lhccp2E", "address": "1800 Augusta Dr #240, Houston, TX 77057, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.42318089999999, 29.7345943], "type": "Point"}, "properties": {"photos": [{"width": 750, "height": 437, "html_attributions": ["<a href=\"https://maps.google.com/maps/contrib/106788706324997826205/photos\">Erika</a>"], "photo_reference": "CoQBdwAAABFNFsxSNqllbm66PuTzB8p3cGMt2FXudnM1nxkelOV79wYj2m9SO0BoB38EOpKDYJXVk86CejZ_ma_Rm9YISWRErhzqfqFvxVrKkj2pneE6BkWf1_dzuUZObp78H61lfeFOZM1YbKc-_bd-2VefVt5HpiLxSck4uCeArelPHiksEhDL0-5Md4eYUmYe9qtCXF-fGhRARiDfw3XMdWJNkgBBktFxfDz_3w"}], "types": ["point_of_interest", "establishment"], "reference": "CmRRAAAA7XlwB9iJHYlUlObhDjpRXjucm7M6VajR0FzaWmdtB4jJLOxnliyB3SUHlpQR1pYfr9hRfiosf15ShZ8DsQ2jY8jlkm5FlpYK3lFedD-T5eR5SmTs_zSWFVQLnRYVQeXyEhCLXrY5eOI4yjbQPXoDVF4iGhQZyMz2fPfAN2DPNQnJRMcS1wGKFg", "name": "Student Conservation Association", "rating": "NA", "id": "1c5ea7722fc0d99e9f7dfca55f5d9078224d51d3", "job_title": "Trinity-Consultants,-Inc.", "place_id": "ChIJQcqBXfDAQIYRErawO-goGj4", "address": "2990 Richmond Ave Suite #400, Houston, TX 77098, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-96.038102, 30.055621], "type": "Point"}, "properties": {"photos": [{"width": 984, "height": 985, "html_attributions": ["<a href=\"https://maps.google.com/maps/contrib/110279808588468038448/photos\">Peckerwood Garden Conservation Foundation</a>"], "photo_reference": "CoQBdwAAAM0NI3D70nChyvabUXYQRjtGM6i0b2kISewTdY43wbejNLWAUD5eBfpOcvPX60HT_cQcuqaovvhDamyRNNWLX-lh2wLj16BO_AFRn_7mjp4Ms-Sa00rcSg3wRDLrT-6sYVql-yIATBx4XD8-f_-LOWyqsBq461WBiEYmRqPKJt3iEhAC46bIiI7KLEhwZd6DxQ8KGhTvb7j_jQRsxfyIOwUpwpz3IBml-w"}], "types": ["park", "point_of_interest", "establishment"], "reference": "CmRRAAAAMgT5-rIm8YoRcYmvL9WhBXVbKwEJSGcH5gEwQV10mRiI7H-4iOM1iuY8b06BFUESLA1HmSMJezoTFF4VQFR-tssQW-b5-PBerzCzgYkj0PjOJCuaxui-wVIER_6B2tTeEhD_3hGzCre5Sd7slvOnEaAmGhQQKaO4IQa9m6CZKlh7OajeL2y9JA", "name": "Peckerwood Garden Conservation Foundation", "rating": "NA", "id": "e618a4c618cd67ce4f5fdc165f640220ab3b53b2", "job_title": "Trinity-Consultants,-Inc.", "place_id": "ChIJmUR7pvHKRoYRIIl0o73bPGE", "address": "20559 Fm 359 Rd, Pine Island, TX 77445, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.64386449999999, 29.7515036], "type": "Point"}, "properties": {"photos": [], "types": ["point_of_interest", "establishment"], "reference": "CmRRAAAAulINKes4lUy6_SiGCpwDXn9RTzuKcXJaGGIgt--14M2l7vw9P5FQLW8ENZFRx_bS8EzJxXijnEaNZQOeCsV85P5Q_SD3xVlBdpXtHPKeVFUhLSA04OIk4W4GbFpjFpThEhBhD0rMqZDwcCmUMQSAxhMXGhQdprO9g8lRYUwuM3osLqWPxkWOmg", "name": "H2O Conservation Technology", "rating": "NA", "id": "30c07988ef8dfc62dac712b9d587daa4a36f2539", "job_title": "Trinity-Consultants,-Inc.", "place_id": "ChIJIWZRKeHKQIYRXxta3wOMGGc", "address": "1725 Hwy 6, Houston, TX 77077, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.5705632, 29.7714443], "type": "Point"}, "properties": {"photos": [{"width": 3024, "height": 4032, "html_attributions": ["<a href=\"https://maps.google.com/maps/contrib/108143329814504597326/photos\">State from Jake farm</a>"], "photo_reference": "CoQBdwAAAPT-Kd3uYCAXNagjKQCWlRtmkFN-xyPEtgEA6RIYN-A8Zc-EURHrn4UMESJeTPNeKButYPVfSah7-_vXlp1pRZWe4_k-MESJ_Ixul_vcXQ3uswolMbO4aIIeNIQSooJEK_gI6n3mpmbYIUhZfPDUU4AyRQxo2SbTyQEOTaP4v8cVEhByfuxU2sU1Bdyrq6dOg16eGhSm3KauxzcPKr7YixX4wrq6JOitlQ"}], "types": ["park", "point_of_interest", "establishment"], "reference": "CmRSAAAA13WiUhFQ-Z4IGDdUmw-Li96C4d6IboqfgvgV-YUFwPclX6XnL0ihy03VV1wXJsVyefogzU-tgC1tctew9BLJV9MFi7dYTJ_QgUF8QOXqvqjvWJdkOEcGxPpbENj3bS5REhBwiuZ4RDXYHD9t6WdYv4u3GhRVfvWh7tXzbgVIuXDNfT7bnLOb8A", "name": "Houston Audubon Society", "rating": 5, "id": "050a5458d86bdd1cee7b09678bd6256d0a20a73e", "job_title": "Trinity-Consultants,-Inc.", "place_id": "ChIJlQOxwVDbQIYR2uX_TZl0TYc", "address": "440 Wilchester Blvd, Houston, TX 77079, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.56820189999999, 29.770778], "type": "Point"}, "properties": {"photos": [{"width": 1800, "height": 1200, "html_attributions": ["<a href=\"https://maps.google.com/maps/contrib/108765250995932379967/photos\">Audubon Docent Guild</a>"], "photo_reference": "CoQBdwAAAKTREY0GjZlX9awMNekMfMAR_od40e_fCOyW3ohwR__lkGaa7UvEBDI61QhxHa_p8R3BTpgr3RhJkq4aAvPt1-pnbunpXe3s_Q--Z4-GLp5ZHrzPJ6pwUadiBMKG5sYobyX_KkPi_xTRQfmcvhtzmJP98ORlx_oNUSW2s9-rEAD3EhA2U4BN9Iq1xFkakvecLmi7GhQNjTd56R2tQu8Cx327DPLfq_NdjQ"}], "types": ["park", "point_of_interest", "establishment"], "reference": "CmRSAAAAKzhWlqNsdTE-IuwrEyEYuel9bgpK2gTnBgUmpGiLLE3ON50ffTWDepBEtY68Z2olcrXo0G9qZJv6PQ8oBVDF1ZuYT6dhUm_bfDohb3qXB3dFS-dUJixrKYiBftD2TQ8LEhCi82NqfSENhtlQ9Xbm9wJ8GhTOTKBLfj-Gb_Wa2F07pd9but8sUQ", "name": "Audubon Docent Guild", "rating": 5, "id": "7ddd5daf76cc4979e2ba6b062322d1c77d5d1c07", "job_title": "Trinity-Consultants,-Inc.", "place_id": "ChIJI9XyNFHbQIYRtwHb8EtTpeU", "address": "440 Wilchester Blvd, Houston, TX 77079, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.44932349999999, 29.7803218], "type": "Point"}, "properties": {"photos": [], "types": ["point_of_interest", "establishment"], "reference": "CmRSAAAAgYHIgKUxuaiif_EE83MG5EJbNyP25NgTOJIxlroyBjEn-SuIUn9R_nf1yua1hnaUi-U9lpTiBYOp8BaJNMFR1oiNt7rwj3aI-SAEsV6HNhfRU0T5CmUaM6413jNtdCdxEhBOSo7_zpRxty7ccMjyRqrGGhSQ5ymJoFM3yTydW6rpPvwJYKRmgA", "name": "Coastal Conservation Association-Tx", "rating": 3, "id": "7258b034e119f31e82320bca6e72781ee9f79d75", "job_title": "Houston-Community-College", "place_id": "ChIJcekacM_GQIYRPzL13cgQrPk", "address": "6919 Portwest Dr #100, Houston, TX 77024, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.47039, 29.655454], "type": "Point"}, "properties": {"photos": [{"width": 5312, "height": 2988, "html_attributions": ["<a href=\"https://maps.google.com/maps/contrib/101184977609161362375/photos\">aug4</a>"], "photo_reference": "CoQBdwAAAOIWC2DmagJFP29-5AhIwEzwWLh3Sz9hV73kdOdIiA7y8u5I_QqK8hbBmrDuewGOabhQgeBDk5xys2K1pJYzIA4PbKQjx6UwMsI6RYYQCLw5N4IoR-mK26iB21FN3-X9cYWaoLBFRFoPNWH7ic5TKrujeYoZZcbu2By0CQI06aUyEhD8GhUB4lQKhn5p8PVY6-PtGhQM2MfoqE7ikGfHib46s0St8N1sgQ"}], "types": ["park", "point_of_interest", "establishment"], "reference": "CmRRAAAA2MuiHpOddT-XLmTLkb_IvIXlOK1fNvRsgIzmPIFo5ZkzdAq2Mz69dIxmqyLbvlwHeZ98gOrwC3Q0r2n_NcxrAxZ9cSNoVqFFLr4Ez96JrSWWrcHmluXxFZ05AtjUGUoPEhBh8W0iA5uj9ZwEJP2mxZvOGhRNjNCps45rBc_JZytXnVeUM5aZig", "name": "Willow Waterhole Greenspace", "rating": 4.3, "id": "0127506e8071350c2d48f0ca56e939045297a0f4", "job_title": "Houston-Community-College", "place_id": "ChIJR6_2zTzqQIYRsA7wExgfDWs", "address": "S Willow Dr, Houston, TX 77035, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.4003322, 29.7388505], "type": "Point"}, "properties": {"photos": [{"width": 1136, "height": 640, "html_attributions": ["<a href=\"https://maps.google.com/maps/contrib/117056878997299689379/photos\">Marisol Brown</a>"], "photo_reference": "CoQBdwAAAEWXBnh5g_sdi83-miwTsv8xyOPWo3aHYgxgYnDNvV2aYe9IeXGpmlgOZwplWeeDswP2kzLRoINnbleEXz8Iv_c6qKIQzaTc-3BntGE-hsRIrHGXSgFKqYikOKRBeCgX68yHFy1fYGF8d1FTpEGLmuJTQuoUOEd90I145OFF5P69EhBgfp6igqUkmq4bUKJuMyghGhRiMxeFFUYO-SntlF7UDMLodu-0Uw"}], "types": ["point_of_interest", "establishment"], "reference": "CmRRAAAARpC98Sgyxlxi4MJUSG4IgVH4HjkU4CngflhwilUEOoZdJX5pI1sXvqRQLRh3g9Od0vwYrTQr6OT_TMC53Kaml1F2SeikDh3u6ksop-CwyGGCMSS06hv9ie3ndJp8qd0jEhBgCtIp7mTVTVKDGw8J4WgFGhSPM774KhVT_LG2QDBrTMA6_Cji3A", "name": "Masters Fine Art Conservation", "rating": 5, "id": "a462c2eef4e22ea319485ae7b84f3d20756cbdd1", "job_title": "Houston-Community-College", "place_id": "ChIJp8u2bZvAQIYRbosnWz6cVmY", "address": "1612 W Alabama St, Houston, TX 77006, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.3876169, 29.794149], "type": "Point"}, "properties": {"photos": [], "types": ["art_gallery", "point_of_interest", "establishment"], "reference": "CmRRAAAARjefryT-PrZhXAqfIpi0h1UrjFq3P8BzDqugDuPlz-6dQM0JHXVS12OsqSAFeS1eYdFGZ-oJt__UHYG5Ey4djM6ESj00psdP2Qq3E7K3Ki8fFQBZBsyhn_WAoPjQGSYbEhCZhn5iVKXj9Mz_TPe21aGPGhTbdpKGIilvUcSZDq3t-v5uOCo3dQ", "name": "Whitten & Proctor Fine Art Conservation", "rating": "NA", "id": "883a8c5ef35ab28e1630235ad65a6b16506a67fa", "job_title": "Houston-Community-College", "place_id": "ChIJ8YuXE6K4QIYRn1SF1hazFEw", "address": "1236 Studewood St, Houston, TX 77008, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.3858767, 29.7300997], "type": "Point"}, "properties": {"photos": [], "types": ["point_of_interest", "establishment"], "reference": "CmRSAAAAj1y6j-Vxhvnr08YOhUGnc5E_ZCFJ7llx8pa7EnhNQfF7L4yh79U7pxMu62iVSD_r2vXcPSgrRQRr43-bYRN85keBFK1ItVU2yJJBDtdVgIWdAr87Uf5NSvwmUi46rmfWEhDKuyV7NHC-6_q7S_Ba0CTWGhTB9VhFoIdrdXvTLxGGfQ5mAWtseg", "name": "St Mark Fine Arts Conservation", "rating": 5, "id": "ea2d4bac6d74716b33f456dff3aae0cc0b43cca3", "job_title": "Houston-Community-College", "place_id": "ChIJKbDEoXm_QIYRcRFBlp0dE8A", "address": "4901 Main St, Houston, TX 77002, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.483218, 29.7482286], "type": "Point"}, "properties": {"photos": [], "types": ["point_of_interest", "establishment"], "reference": "CmRRAAAA7OSpI229G7nHa4la6IL-ssipsfwcXwP4VhYQIXhO8V7XG_5xv_AEFcy5Eroqd2pf15E7N3OlUREk9PKZ46slDihwVXmUh2t1N6apJbwfAguBeKHgrzKNyEnjpT3mUlQpEhCzeo6dAftr-cAct6F1q9ipGhQf1BkEnbLOB_Y1vaifqnqCS6ko4g", "name": "The Nature Conservancy", "rating": "NA", "id": "90af6fb9fb926dde9f7103577cebc4150bbb1dec", "job_title": "Houston-Community-College", "place_id": "ChIJq-m4EX3AQIYRJkn4Lhccp2E", "address": "1800 Augusta Dr #240, Houston, TX 77057, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.42318089999999, 29.7345943], "type": "Point"}, "properties": {"photos": [{"width": 750, "height": 437, "html_attributions": ["<a href=\"https://maps.google.com/maps/contrib/106788706324997826205/photos\">Erika</a>"], "photo_reference": "CoQBdwAAAEoitZhwnQQO113-1-KFbNY8mC7eQ0MnLAw5BH7wTmdKZQLyQfewxLLbtLGm5ilSwG5ydhJzVm9eZuvS2xL5AlX-T0TlrnxTuv11gxVmpMEZlMwEmz4os7vpy6En_0JZ-XZDIoxeXjWnIr97UhZ531OZbfqi7zywkNY677BKZPlSEhAxi6lMvBr9pdpNoNfX9V9lGhR94LrqpLszyYao8z0rcOGE7yHTEw"}], "types": ["point_of_interest", "establishment"], "reference": "CmRRAAAAjzJoeRe6qw-T5dh45zZmGAaFOIpQYHbrrYe2po6AqvTwB0joDAAoYWSB12z1S210Zwd9N0wT0jPee1RhKSgnBw6wqeqOsWhBtTy1edFarR-wyTTefSRSmJDBQ7Uc6wPAEhC9QTaHwJmKDgtIIROPgyFhGhRLDkmh3PHDnW75-AWlTdsbDNIRtg", "name": "Student Conservation Association", "rating": "NA", "id": "1c5ea7722fc0d99e9f7dfca55f5d9078224d51d3", "job_title": "Houston-Community-College", "place_id": "ChIJQcqBXfDAQIYRErawO-goGj4", "address": "2990 Richmond Ave Suite #400, Houston, TX 77098, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-96.038102, 30.055621], "type": "Point"}, "properties": {"photos": [{"width": 984, "height": 985, "html_attributions": ["<a href=\"https://maps.google.com/maps/contrib/110279808588468038448/photos\">Peckerwood Garden Conservation Foundation</a>"], "photo_reference": "CoQBdwAAAA0mtnDYCN23woM334A2xn7zSvo8unSnOsbqQFV1kJDlnijPrfsA4r7BZk4fKn136-jaSZJj9d9doC06_qKZLr7Iu52633rWk6IFGFFOBc1sqz3o5ZWRajBd7tQ7ygacIvVe-0g6xr7kyLQ0l4tZUBHS2dbjG3t_1SEQ-dAXJteYEhDepTQQyfJp6zyusAN2m8ezGhSibYmp0UoAslcC8-hCW-GoRM9hCg"}], "types": ["park", "point_of_interest", "establishment"], "reference": "CmRRAAAAOz4SdMoyhPaFucxX5MFzWqfRFin7BbfMNp-AaOtza1LyWOMt0vKTy5Wm0GBboLUILajeJ0keTV7y66mmdyqa207v95wdnhBmGBjOedlDX0bHIZhumCndoVLTJLO7Jg4AEhCn1QTdGqsOOMEzDRddUqQOGhQh5q0BQpA7zNSSldQJ6hD4r9vnUg", "name": "Peckerwood Garden Conservation Foundation", "rating": "NA", "id": "e618a4c618cd67ce4f5fdc165f640220ab3b53b2", "job_title": "Houston-Community-College", "place_id": "ChIJmUR7pvHKRoYRIIl0o73bPGE", "address": "20559 Fm 359 Rd, Pine Island, TX 77445, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.64386449999999, 29.7515036], "type": "Point"}, "properties": {"photos": [], "types": ["point_of_interest", "establishment"], "reference": "CmRRAAAA1riROTmiA8ZFnTbID1CFJzv-W1pH8pmBjSqJ_mYgciMC65tlfWoObndVMkMrbQ9B1xg3ZYrn0dDA4RSaEX3LhaRd4Kin8GXQcb89d1bflLxLxQyIlc92spW1MWETS8mGEhAQX38OacsxMtLzcVofLB5QGhRtb7JWX-qe-MbaX8wgS68AgogBHQ", "name": "H2O Conservation Technology", "rating": "NA", "id": "30c07988ef8dfc62dac712b9d587daa4a36f2539", "job_title": "Houston-Community-College", "place_id": "ChIJIWZRKeHKQIYRXxta3wOMGGc", "address": "1725 Hwy 6, Houston, TX 77077, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.5705632, 29.7714443], "type": "Point"}, "properties": {"photos": [{"width": 3024, "height": 4032, "html_attributions": ["<a href=\"https://maps.google.com/maps/contrib/108143329814504597326/photos\">State from Jake farm</a>"], "photo_reference": "CoQBdwAAALvVYXghKNnQ0jtSHYpKei_f_8bC-C6qbUOEGuy8HmkhB6fDsa0jZgZT8lN_lIJMcu6JUqqaJcqN24FsYeCJqvs9kw8VgcYFbF1FsIAAbjRwdeBzOboSN_67o_ssFOIBCYC9q_ZqyLs_UAsmdi5ERMaz9ZWhWAxhlr5TpZGxDZuzEhAnFCucMiNu2rCppRONL1bjGhT3ONeKWeVr_hnTvodlATcPMg7WkA"}], "types": ["park", "point_of_interest", "establishment"], "reference": "CmRSAAAAQiOk_jhUdr9f4ktSbKhHxicseWap7dB1NOqne7SsC0kned8e1ylsHkw_tnfl7rYytA4i61dvPfT8984TwMTo5Wp_pmbeTkx1brZoo4jk-eCxXTD4zpdneVKrO4xOYcwGEhDO-QAv_D2G42qkXQQiwMNiGhTcgX_RJzHtqAKYtpFUfsVqaqFpWg", "name": "Houston Audubon Society", "rating": 5, "id": "050a5458d86bdd1cee7b09678bd6256d0a20a73e", "job_title": "Houston-Community-College", "place_id": "ChIJlQOxwVDbQIYR2uX_TZl0TYc", "address": "440 Wilchester Blvd, Houston, TX 77079, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.56820189999999, 29.770778], "type": "Point"}, "properties": {"photos": [{"width": 1800, "height": 1200, "html_attributions": ["<a href=\"https://maps.google.com/maps/contrib/108765250995932379967/photos\">Audubon Docent Guild</a>"], "photo_reference": "CoQBdwAAAKYD-T1zQk3NTkmb499c8wbP4n8_fte6KcUEosjvTOWZDA-zD0cvZX5_PAIj_xcRI6xQJQKLBLFJuBya0AFVU4LH6kRMwq18DafP8XZhQXW-9hUPF0-4XylwhJbgpxdPjzDV5B-02q-GVGBo0rJhlCqWYT83vpBDl4hCtHl1cG0rEhABxWtbYSkJKuE1_xZVOyAuGhSP6CWCB_NuhEEmEkQvCKge4Qf3BA"}], "types": ["park", "point_of_interest", "establishment"], "reference": "CmRSAAAAxRxBirHCKVsiStCggHQGrUfmvTFrjkS43HcENLA1f_8pfPEIrTAfYMwrDxFckY75xN_YuDt6BUE-zFsWwJD0pYKaei-bDShU3ps4ApTIFtdlna3LuVX84JdSQl1R-E9iEhDGjbZXKQg34rSg1Vz8Z857GhRcfvHhTUAm7AQJPCviSFMTgJrVKQ", "name": "Audubon Docent Guild", "rating": 5, "id": "7ddd5daf76cc4979e2ba6b062322d1c77d5d1c07", "job_title": "Houston-Community-College", "place_id": "ChIJI9XyNFHbQIYRtwHb8EtTpeU", "address": "440 Wilchester Blvd, Houston, TX 77079, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.44932349999999, 29.7803218], "type": "Point"}, "properties": {"photos": [], "types": ["point_of_interest", "establishment"], "reference": "CmRSAAAA2pcHOEHZ71QUUlJmEep3F3nwElQoLG0AKHunN8UxqLc3zAj9fEhAvNhNncyWplxSwytGLhAAQXEP7b6EkqGQrzubde9hMitTAaG2aLQXwsFdiCTBiuWA3IKwOFWCSHhsEhB5mi_U0--6ezidV9IVsn5VGhRAa7tqpVxmMj2DY5Kvf7wswsYSEQ", "name": "Coastal Conservation Association-Tx", "rating": 3, "id": "7258b034e119f31e82320bca6e72781ee9f79d75", "job_title": "Dbr-Engineering-Consultants,-Inc.", "place_id": "ChIJcekacM_GQIYRPzL13cgQrPk", "address": "6919 Portwest Dr #100, Houston, TX 77024, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.47039, 29.655454], "type": "Point"}, "properties": {"photos": [{"width": 5312, "height": 2988, "html_attributions": ["<a href=\"https://maps.google.com/maps/contrib/101184977609161362375/photos\">aug4</a>"], "photo_reference": "CoQBdwAAAD6bCjrSGDLkRPcI3LgjEIuaefIlaZjv_S5sD8oOZkGP8KpfF78UIPzfmFyXgsZ30bji3KSWwjiZb3F9gGDMdgX-JoBLtOmfD4IAED4DHshzqXVDbMvKLjyHyPFWdHHgpy_9EcIaQRARlstmx8xDL3nR2ZZDl-rOs27Iv7F1IcWcEhDZlbiv6iMpJNkYt2qgHlu6GhQTBwa2nW3QoRZkdLO4EjnspW4EqQ"}], "types": ["park", "point_of_interest", "establishment"], "reference": "CmRRAAAAIvoRMwJajQOvHIjZl_-ckZMIt4AKreft-0eNAMv-1Bdy7v1v08zFK1sA-1Nbgb_h_B71agxzaDuXKpOL9cy_OD0sz_efp6pqlQXYNR0V_9RdiXS7lvVZkpSiJVgjtufSEhCzuzvnDh7C1ikosYXTrhAYGhQ32UHhTf8gSx2mp3Iu8U0KKdSycw", "name": "Willow Waterhole Greenspace", "rating": 4.3, "id": "0127506e8071350c2d48f0ca56e939045297a0f4", "job_title": "Dbr-Engineering-Consultants,-Inc.", "place_id": "ChIJR6_2zTzqQIYRsA7wExgfDWs", "address": "S Willow Dr, Houston, TX 77035, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.4003322, 29.7388505], "type": "Point"}, "properties": {"photos": [{"width": 1136, "height": 640, "html_attributions": ["<a href=\"https://maps.google.com/maps/contrib/117056878997299689379/photos\">Marisol Brown</a>"], "photo_reference": "CoQBdwAAAL_NcvAatKGkTXZvT4DtStF1T6qm9ZQ1Iaw_wntd0YevANrRPlp3_ibyrecHoaSrMAYeMgrxhQovqJQ8JCwZZQZplkKMuZCfYFvpRNeJtNYbxeW8DpQ28axkAUb0lDh_yLK5FaFVF2A5Ow0eTlauWXLnxdfnWwyCRYT9FILzLoXjEhC9D6fZgRfVXdPF_6KWO7c7GhTjd1Kc63yEQS_hyuFtOC4OtlVTwQ"}], "types": ["point_of_interest", "establishment"], "reference": "CmRRAAAAewl0aDS8Ui9RQEfzKA-kVCcoosbEiBnPruyzRzV7JPBiZAx5XhR3TH_t3COCGjgEnwgSBCHAepQL034JC72zjJiYziGNoR_dYfDi8aYW3JjWO5WgNn7AZX-WYnBS6D7cEhBmYpex4HXWVxvqcMvBzmpZGhRARhGnNfSrt_PDQKvDqbHspEscog", "name": "Masters Fine Art Conservation", "rating": 5, "id": "a462c2eef4e22ea319485ae7b84f3d20756cbdd1", "job_title": "Dbr-Engineering-Consultants,-Inc.", "place_id": "ChIJp8u2bZvAQIYRbosnWz6cVmY", "address": "1612 W Alabama St, Houston, TX 77006, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.3876169, 29.794149], "type": "Point"}, "properties": {"photos": [], "types": ["art_gallery", "point_of_interest", "establishment"], "reference": "CmRRAAAA-ugbVsnazo4wKtKla7BwJkrDld0lw-DgGH_v-aR5HoW1hZZNxJN29YSYGjuQNt1aInyHsmzUB7qjNd4-j8vDKYvWx_SL5zqdgbBxw5lK3fDRYoJRd4sKHXwwKA7tag9NEhA6jMiQVBvWsS3ptmyNJMmUGhR3FAbsKywVSNE_kvWZhPXi0qZ8fQ", "name": "Whitten & Proctor Fine Art Conservation", "rating": "NA", "id": "883a8c5ef35ab28e1630235ad65a6b16506a67fa", "job_title": "Dbr-Engineering-Consultants,-Inc.", "place_id": "ChIJ8YuXE6K4QIYRn1SF1hazFEw", "address": "1236 Studewood St, Houston, TX 77008, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.3858767, 29.7300997], "type": "Point"}, "properties": {"photos": [], "types": ["point_of_interest", "establishment"], "reference": "CmRSAAAALLBzWSaaCxP1N8HorGBOScDbeIl5deST_cTcuO0J11AFqjlQpR6vrHBh9Rl_cKY2SkZAaX8bv4M-9G9MbJOusVxwxbB44-L_M4XxCli5lT6q1MuraAoHMZ49oqud6G_PEhB9Hy2G-GGdKbX_nRJ7JgqUGhQF_6SS4z0MEuutgJDv_-wqR1sDTA", "name": "St Mark Fine Arts Conservation", "rating": 5, "id": "ea2d4bac6d74716b33f456dff3aae0cc0b43cca3", "job_title": "Dbr-Engineering-Consultants,-Inc.", "place_id": "ChIJKbDEoXm_QIYRcRFBlp0dE8A", "address": "4901 Main St, Houston, TX 77002, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.483218, 29.7482286], "type": "Point"}, "properties": {"photos": [], "types": ["point_of_interest", "establishment"], "reference": "CmRRAAAAyA3TfLJ5jr8Wi7mJlzsF-TwbBo1N4w7B5LxcpnJ5G5s0pWy918x-aHqXH9_iG4uAvRLlBRKmXYA4D1wsWZVoEzJtO5spcuHwG3M_A0PfAJr2dNgFXjPFTRGnuHiyvCMMEhBb0l0ehfAXB3pNe-KHgQrAGhQNCHO9TOGa_N3_R7oohZqZ2HAMvQ", "name": "The Nature Conservancy", "rating": "NA", "id": "90af6fb9fb926dde9f7103577cebc4150bbb1dec", "job_title": "Dbr-Engineering-Consultants,-Inc.", "place_id": "ChIJq-m4EX3AQIYRJkn4Lhccp2E", "address": "1800 Augusta Dr #240, Houston, TX 77057, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.42318089999999, 29.7345943], "type": "Point"}, "properties": {"photos": [{"width": 750, "height": 437, "html_attributions": ["<a href=\"https://maps.google.com/maps/contrib/106788706324997826205/photos\">Erika</a>"], "photo_reference": "CoQBdwAAALyOHz767Kzy3qR-mMCV3CKmoeHWea7PV3BBZARiQQgvfRsChhxiMYiLiTzcq497x8Kb4bjINFiJIGSnSV_P8w7KKLk5gDMJ_PlAsya5Rel4chtLr4FGlEVhQIbXBww02B-5euxwOCSQ7oxIvPHbSJxpjmRc5dkythCRx3FEogVNEhAzbzerToNeXQZmLK9rj0E0GhRPokSsOLkuVLte6-voxQ3paqdphg"}], "types": ["point_of_interest", "establishment"], "reference": "CmRRAAAAARIK5FFjRjsRifVGJQ-FSpeRhIiwdOLr79Lh_tfRP5BzG3qluBbQ8GBtfBF0nrVXCjD7Kmz5WsHVkGczT4-2Umv7mEaa4Jz1VOt4M4JDr9qur7KZkJJHtKzLNWYUKEqCEhBQN-KIcHLPrBPTzLoZYNlOGhQkOmitPQR5oj_TssxtoqG3Cm8aNg", "name": "Student Conservation Association", "rating": "NA", "id": "1c5ea7722fc0d99e9f7dfca55f5d9078224d51d3", "job_title": "Dbr-Engineering-Consultants,-Inc.", "place_id": "ChIJQcqBXfDAQIYRErawO-goGj4", "address": "2990 Richmond Ave Suite #400, Houston, TX 77098, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-96.038102, 30.055621], "type": "Point"}, "properties": {"photos": [{"width": 984, "height": 985, "html_attributions": ["<a href=\"https://maps.google.com/maps/contrib/110279808588468038448/photos\">Peckerwood Garden Conservation Foundation</a>"], "photo_reference": "CoQBdwAAAFGB_QGMn_Kt8E_IMP9BABhuBmlQYqAkLvti-03SFbfg_EWKOtdKLitWU3yDr_cfELOGUrn_YGxAjGoWKUgh6iCVUSFlyn1T9qmx_M-l-gf1tEwrf5vSrwPDMa3NskHiQaJgJZkbz6X0T6PyoQt0UxK3uXVr1d9Zk3nuO_PFg1K-EhAX52lF6cP3PrjFmlb_ZmXkGhSBe__FxOuvzz-vQtM3HJ37A8zX3g"}], "types": ["park", "point_of_interest", "establishment"], "reference": "CmRRAAAAY4wnFe4oPIBkKY79i0H2PkJRAqxbsY9pHurt4aVW0F56v1pduXiKQQ5kdfqcCpy56lYk4n9CpDfuhFEI1HP6RECIAs6pI4f4N6hM0ok10iMPJ4VtUZJbivv_Ovtft3-REhCHwaunD9iILRA1RPib8QOUGhTODg84KoDXHu2c7MOzjCvAA5aanw", "name": "Peckerwood Garden Conservation Foundation", "rating": "NA", "id": "e618a4c618cd67ce4f5fdc165f640220ab3b53b2", "job_title": "Dbr-Engineering-Consultants,-Inc.", "place_id": "ChIJmUR7pvHKRoYRIIl0o73bPGE", "address": "20559 Fm 359 Rd, Pine Island, TX 77445, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.64386449999999, 29.7515036], "type": "Point"}, "properties": {"photos": [], "types": ["point_of_interest", "establishment"], "reference": "CmRRAAAA1dVZNUhT8s9Rv67gMqzCBkyLa9m7fbINd4sOf0A0DfKABaAG-XMPMEWC6yqLxXbNgdQ76v_6Ow_1R9bS6XSDPuBs4QvyoJwlxMS4EXONDh1LxQda7NtBICc3UzuWE73QEhCQBRz5ZiV4Y3DnvF2Tao1DGhRj4CdWcU9ZuA65HtMAjV815yFqVw", "name": "H2O Conservation Technology", "rating": "NA", "id": "30c07988ef8dfc62dac712b9d587daa4a36f2539", "job_title": "Dbr-Engineering-Consultants,-Inc.", "place_id": "ChIJIWZRKeHKQIYRXxta3wOMGGc", "address": "1725 Hwy 6, Houston, TX 77077, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.5705632, 29.7714443], "type": "Point"}, "properties": {"photos": [{"width": 3024, "height": 4032, "html_attributions": ["<a href=\"https://maps.google.com/maps/contrib/108143329814504597326/photos\">State from Jake farm</a>"], "photo_reference": "CoQBdwAAAFYIZQFkqm8uB1-iz8Hod0eeJo5yFZ0jhqhsmJhEPL04wto0hbMNS0WWSp_eZSVKoWC3sFOvWYhnnVp3fbPYU7KUK2EnWBkKYlp8MD5e2yfzgDbSy6oqQIpabqcn9N-QfCEt5CICG1Ywj7KqXEessU3-oIk197RKffQB4qu3toHGEhAf5i7mcGXeYEZ35kU4PQTrGhTcBnEdVB0z11ly9n9ZNX3enekNLQ"}], "types": ["park", "point_of_interest", "establishment"], "reference": "CmRSAAAA5cM9HRH7Ak9h7ZY5zFxVnWozlLqZJpb9ThqILHRP5z5OqZ7c10zCGeBn-6zwE0AigA8sjLSXY1teVe9XbAlnqsnypKT5aCT4fqxembd2wEO9usXelGfKS32llHad7W3pEhCWPPDE7-ntPEyBRpyqoC4-GhSm9cBsthmXTjKN-vYPTmRHBEKdxQ", "name": "Houston Audubon Society", "rating": 5, "id": "050a5458d86bdd1cee7b09678bd6256d0a20a73e", "job_title": "Dbr-Engineering-Consultants,-Inc.", "place_id": "ChIJlQOxwVDbQIYR2uX_TZl0TYc", "address": "440 Wilchester Blvd, Houston, TX 77079, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.56820189999999, 29.770778], "type": "Point"}, "properties": {"photos": [{"width": 1800, "height": 1200, "html_attributions": ["<a href=\"https://maps.google.com/maps/contrib/108765250995932379967/photos\">Audubon Docent Guild</a>"], "photo_reference": "CoQBdwAAAIZ8UlFjUOO44Cjchunu74g3Mvu2Y_QXGIMQMsgc7xLGgBvOLkiwRnFr4F-zNStigt_lBifS7LCH6w0z62yuFkIt7MxMHSb2M0Y3H25MeM_qB03GxGtgx_KQdGHKCO2zvcZgyaEl2iKY3HAm6uEA7geyOabnNymipZVGe6upLB3fEhDdPV3fTUJf0dAgRhktAvrKGhTZVal_usAHKUxgTi03fVAqueJ6Ww"}], "types": ["park", "point_of_interest", "establishment"], "reference": "CmRSAAAAC1MNclWxZFoShuCCKZIw6s4dYIuabOrLeghG-bayoga35dw-hLX0bvCQwcyhEVfEuEMGpO1ohHOI2atHP3itBHfdYDOPUTJINYB_YqEhJoB9Ltd-L1KL7GaVoY3z7Pw0EhBMcNyGM_-tiJ4_8KzaKq3MGhQy_teBwePIY8Q33QuN155z_WrQrw", "name": "Audubon Docent Guild", "rating": 5, "id": "7ddd5daf76cc4979e2ba6b062322d1c77d5d1c07", "job_title": "Dbr-Engineering-Consultants,-Inc.", "place_id": "ChIJI9XyNFHbQIYRtwHb8EtTpeU", "address": "440 Wilchester Blvd, Houston, TX 77079, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.44932349999999, 29.7803218], "type": "Point"}, "properties": {"photos": [], "types": ["point_of_interest", "establishment"], "reference": "CmRSAAAA-6-HxmEGe5dO6Xogzb7NWG5xrYaddMgfrv3WkpeABgpggtuiAbHv0Q2LMtVZ2GbDoRhOvqdSSo8u1nshOiVKV0n61ZYXfMo9-lr38KZZQuZvO8-0SmOWd1NFMlslMeFvEhD05c377_q4UmMwSklDy4SZGhRF7kFCTf6RHw_WmgMsOdL4nSE-Bg", "name": "Coastal Conservation Association-Tx", "rating": 3, "id": "7258b034e119f31e82320bca6e72781ee9f79d75", "job_title": "Tilson-Built-Company", "place_id": "ChIJcekacM_GQIYRPzL13cgQrPk", "address": "6919 Portwest Dr #100, Houston, TX 77024, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.47039, 29.655454], "type": "Point"}, "properties": {"photos": [{"width": 5312, "height": 2988, "html_attributions": ["<a href=\"https://maps.google.com/maps/contrib/101184977609161362375/photos\">aug4</a>"], "photo_reference": "CoQBdwAAABafqiE9QIc3Ga971h8vEtAHx7G-CuewNvL5eRcds6Xfb62uzY9wRqrgwkIfAL3p_Swbk220wYXJz2pnPKLL_NNUHDkKdhP66xbTxVrDrMHPXVg4Tf1_eFIhSrfKShM8RycluWKqzhGSQA-VcXZNadvKJL8GyhiC3GSJp8bWWlOQEhCxfzbvXcX8aVC_S_lhMkMIGhRmnlVCUmE4r9sznwIRaWndIDenhw"}], "types": ["park", "point_of_interest", "establishment"], "reference": "CmRRAAAAqsMIb6yTOhc0aB-lvehN8KUgrmVuQ4jbi8Os9Hkv-4FwOnR-deV7g84Jw9Mf2Q0OvwQ7fcf6gvIhFNABPv2ZEVTXmj8FVENPk5pX-YhORXK5cdQy3Zgzor79eRS4hzP4EhBQATr00JdnZ5iFQo_G-OQ2GhQEOU1yERFL5-Lk6NJk5I2qSX8_qQ", "name": "Willow Waterhole Greenspace", "rating": 4.3, "id": "0127506e8071350c2d48f0ca56e939045297a0f4", "job_title": "Tilson-Built-Company", "place_id": "ChIJR6_2zTzqQIYRsA7wExgfDWs", "address": "S Willow Dr, Houston, TX 77035, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.4003322, 29.7388505], "type": "Point"}, "properties": {"photos": [{"width": 1136, "height": 640, "html_attributions": ["<a href=\"https://maps.google.com/maps/contrib/117056878997299689379/photos\">Marisol Brown</a>"], "photo_reference": "CoQBdwAAAPNX6uSTNdSdbQh5M590S72tSeQeirzTEc7bRwh4M4cuDTQDuCtH6thmYs5ATMWTW6h8VuSb4R2g6dzig5JnFloWiXc1IEF_SAyC5Lr8-b-xsFwPCl9vNKQGMUkzOs5njUojiB0QWW1kwsN5Yj9_VDvJJMvaBSwJv8xo96SK2lYdEhBrPiz-jQ49njJVPiKRHxqEGhQUsuo7Bjr6XcwnxI3DpPoPY963zw"}], "types": ["point_of_interest", "establishment"], "reference": "CmRRAAAAGgYMI2d8DBRpMf623sVDk1Lc5g6geIK4cIXq0VBbkGQwOd2JnZ-ASIa1qQY6_PLn2KOiPAhXbr6MdtMuK1NSjWm0sjeq12GmHPMXxqZzCxOOj9HtKGxiMj4N6HTtO4h5EhCJMA73wtEtn7kMmzwWM1baGhSBdFQGGFzPcPLNop0_NfR2km7H0Q", "name": "Masters Fine Art Conservation", "rating": 5, "id": "a462c2eef4e22ea319485ae7b84f3d20756cbdd1", "job_title": "Tilson-Built-Company", "place_id": "ChIJp8u2bZvAQIYRbosnWz6cVmY", "address": "1612 W Alabama St, Houston, TX 77006, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.3876169, 29.794149], "type": "Point"}, "properties": {"photos": [], "types": ["art_gallery", "point_of_interest", "establishment"], "reference": "CmRRAAAAkVt_aBw7NGxvZ01dFD1Y4YfuuX1y-VwzjoUAD9hcULbDnw-AFTn9c01Eox-tiQVokSsm9jgpg_Vy-43VXsqfFPH2QtlCtreIvIlpn2UTk_qBgU5tt_NS_w1wYb3IsnWKEhDA-I2BiKrqnPPik4npRCJ3GhTNiC-VavenTBSeTLQcnGEnM_IRIA", "name": "Whitten & Proctor Fine Art Conservation", "rating": "NA", "id": "883a8c5ef35ab28e1630235ad65a6b16506a67fa", "job_title": "Tilson-Built-Company", "place_id": "ChIJ8YuXE6K4QIYRn1SF1hazFEw", "address": "1236 Studewood St, Houston, TX 77008, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.3858767, 29.7300997], "type": "Point"}, "properties": {"photos": [], "types": ["point_of_interest", "establishment"], "reference": "CmRSAAAARSgCouHR4mum3uZEnrDD7MFSqUrHoNGSL3EaJcvinp1LocQEL-edpmohTvyfKQQp_olkwtWfJUc0sR-KUhgHIDioxPbLG5VZ5D5JZl1YK7v4h_luvAY8P7iXkDpjHsf1EhCooWV_Zcq3tm08LvegJxVCGhTN17SW66rGEJVXD7sX2MPE7HoySA", "name": "St Mark Fine Arts Conservation", "rating": 5, "id": "ea2d4bac6d74716b33f456dff3aae0cc0b43cca3", "job_title": "Tilson-Built-Company", "place_id": "ChIJKbDEoXm_QIYRcRFBlp0dE8A", "address": "4901 Main St, Houston, TX 77002, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.483218, 29.7482286], "type": "Point"}, "properties": {"photos": [], "types": ["point_of_interest", "establishment"], "reference": "CmRRAAAA2_G8D6V_gHCNLSAaK0eEStlaoySky8tXb4TyIKAOaC9a2vl-lvYMoVVBD5Oqk41jjw3RtJrtL4_Xv8auyvenFAxPdlkotRusBLMlO6QBqEiPUYWzgD3Iqpt0-xioZl0kEhDNgje7n6g_xZtC9GmLVxFaGhStpriL-SSKmB7VzPO7TUFEHanmrg", "name": "The Nature Conservancy", "rating": "NA", "id": "90af6fb9fb926dde9f7103577cebc4150bbb1dec", "job_title": "Tilson-Built-Company", "place_id": "ChIJq-m4EX3AQIYRJkn4Lhccp2E", "address": "1800 Augusta Dr #240, Houston, TX 77057, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.42318089999999, 29.7345943], "type": "Point"}, "properties": {"photos": [{"width": 750, "height": 437, "html_attributions": ["<a href=\"https://maps.google.com/maps/contrib/106788706324997826205/photos\">Erika</a>"], "photo_reference": "CoQBdwAAAPRS1pUW5vVn31eRPKcWah9WS3twxgcSOx-bCe4QmWbcnEJ7_2hsG68Pf45eWEum56auyzDLHjkGvn1XhnvuUGT-A3j8qi56Jj9_Z1v-Kt9FDMyPWlRrPOAviHXGNt6CzQ_kv-Di33pB_5hPZOYnWufiNOdBNcn317AXQc80wY-XEhARzzi09ndjrOduQGrOwMlUGhSaJ6CfUjXRvtf9-MjTk6fn0zZ0OA"}], "types": ["point_of_interest", "establishment"], "reference": "CmRRAAAA55DvXcFmupaS6c_5RC2WqHOderYmQ_RLlbEeyzgsxQIKmRAxS9muclb-GNoir5V_6oO6n-bIFkdRmNK8XrouaVncF3mLYM6XiMetwqoUnDEyAxoYDh8hmjW9yZo3yaH5EhCJ9lx9dH-mZbUaigJyCFBmGhRljkKab-kA4z_f3AZMyYilJ4Z3sg", "name": "Student Conservation Association", "rating": "NA", "id": "1c5ea7722fc0d99e9f7dfca55f5d9078224d51d3", "job_title": "Tilson-Built-Company", "place_id": "ChIJQcqBXfDAQIYRErawO-goGj4", "address": "2990 Richmond Ave Suite #400, Houston, TX 77098, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-96.038102, 30.055621], "type": "Point"}, "properties": {"photos": [{"width": 984, "height": 985, "html_attributions": ["<a href=\"https://maps.google.com/maps/contrib/110279808588468038448/photos\">Peckerwood Garden Conservation Foundation</a>"], "photo_reference": "CoQBdwAAAAo7-TtSodK0gOUNicZF8Xk3qH_JAxeGVQZ8n9R_3mQhxD29g5rEsKPQvtboOLyYzQGi_wgDPK7qsJPZM79Kk2BIMgsK4EzAjY14-NMBDVO6Hvst7Th2fYLsttqe1iXsUTD9Uskfg2WTrdQYGtXgHRrUFA-xpG9PKXWKpiQiThp_EhBu1HvNg3gyBXydsybvo2ZvGhTFOqxmkHcxNgeu3SGzQZvIgLk3cw"}], "types": ["park", "point_of_interest", "establishment"], "reference": "CmRRAAAABCfDdKEqnLKe6wxOIeWptPuO1h8rEL7c23WPY_VkQ86BP8gjVa7XB6kt053tOgoEoCS_aFgczjC5o0KuPwVwicmCkpwHt96UpYW_QSp6WEjuunlDSycinN_OnOrVZrJsEhD30_SjQr7jH5H0YQZoDTflGhSMkVzjtyZynN4es5_JXiaiwqWa_A", "name": "Peckerwood Garden Conservation Foundation", "rating": "NA", "id": "e618a4c618cd67ce4f5fdc165f640220ab3b53b2", "job_title": "Tilson-Built-Company", "place_id": "ChIJmUR7pvHKRoYRIIl0o73bPGE", "address": "20559 Fm 359 Rd, Pine Island, TX 77445, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.64386449999999, 29.7515036], "type": "Point"}, "properties": {"photos": [], "types": ["point_of_interest", "establishment"], "reference": "CmRRAAAACw4AVIYvywf4uRX0gyaZC1p1HeLDJki3AxXWoRowUBEe4Bg7xmhHC8-NRMnZCQEaa9reQCASb8AJkhjeQijMdjKMDDhUG-WKGPieDa9xzqrNdeMBYAnIrvjgttO4ngpDEhALIbJVeFTphrOCHpVg1TRPGhS7UobcDQPH0xWm1tULX2PagDTYBg", "name": "H2O Conservation Technology", "rating": "NA", "id": "30c07988ef8dfc62dac712b9d587daa4a36f2539", "job_title": "Tilson-Built-Company", "place_id": "ChIJIWZRKeHKQIYRXxta3wOMGGc", "address": "1725 Hwy 6, Houston, TX 77077, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.5705632, 29.7714443], "type": "Point"}, "properties": {"photos": [{"width": 3024, "height": 4032, "html_attributions": ["<a href=\"https://maps.google.com/maps/contrib/108143329814504597326/photos\">State from Jake farm</a>"], "photo_reference": "CoQBdwAAAOr3C_gOFQd5lyCK9khBas_G5_O3iag_9vHQMBNrOtFQYxjEvQfgma5JfMpfoARmEGtw-9W2W5_aNrldRtmp6thldqEYYibONNZui6pAb1him8607DQKkpRAkjon4aEvga43Rg3jJtKc-jKbOtMrmAS7PAPgFbGTGreIdibf3YdrEhDE4UMiHpJeyAhlVFmWCV8BGhR4Bg_GL5j_vpwaneYRrGtgTKvRAA"}], "types": ["park", "point_of_interest", "establishment"], "reference": "CmRSAAAAnEFxjvFbKFvUNx55mkPqqQY49fyGmvsFUXYpQJ2rMe8spNjAB6F-2ujdFrFwbelnxU83FNSRtFHZ1oRKyiCITYm99nQ6N4CaFHu7YRM24F3Kh_s14wm4pdZSlDk7h5v3EhDkISdW0ukIeIM0OOLtow-nGhQYd1JMW6kMH1XBmkY5c_p3zQegQw", "name": "Houston Audubon Society", "rating": 5, "id": "050a5458d86bdd1cee7b09678bd6256d0a20a73e", "job_title": "Tilson-Built-Company", "place_id": "ChIJlQOxwVDbQIYR2uX_TZl0TYc", "address": "440 Wilchester Blvd, Houston, TX 77079, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.56820189999999, 29.770778], "type": "Point"}, "properties": {"photos": [{"width": 1800, "height": 1200, "html_attributions": ["<a href=\"https://maps.google.com/maps/contrib/108765250995932379967/photos\">Audubon Docent Guild</a>"], "photo_reference": "CoQBdwAAAL3Wfnt0nbsGQWfFqOqcPzcl5YHnjfeorOm6qbyDfaGjeINUwZoX1fdPr1AUlsGWkRwPEK-N6kgha8rqg2WO0jYPvs60A-izzfEvy5F8kSxSZplVbeWffzy9XGsYkcTfIq0K2bBEh1JSNI7OjneiAnJShPvlTV1Kq_OBjVZW4IG_EhAVnF8nZd8_XmSrjJdrwJraGhSSdubFmubBd4AGymJsK8zWlRWj5g"}], "types": ["park", "point_of_interest", "establishment"], "reference": "CmRSAAAA-12ayBDf6lZ7B2JhUJMNaspyFbtNrinv87HOXZCdLZOUSFDM0XVav6GyihBosAvQvMDFDMD3E1qA9ZbEv221v_ksGM1bO0EzVYFO79Wp56LQPXLN5yVeXOXJWTQcda_5EhCYaiy9q7FAxITsBvJkge3vGhQOO5YLN2dI5Cs9TKGocXCD6tULSQ", "name": "Audubon Docent Guild", "rating": 5, "id": "7ddd5daf76cc4979e2ba6b062322d1c77d5d1c07", "job_title": "Tilson-Built-Company", "place_id": "ChIJI9XyNFHbQIYRtwHb8EtTpeU", "address": "440 Wilchester Blvd, Houston, TX 77079, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.44932349999999, 29.7803218], "type": "Point"}, "properties": {"photos": [], "types": ["point_of_interest", "establishment"], "reference": "CmRSAAAAqVRFoA7YP4vizLZo17MyvhQYCD1qT9yF2aI5PRqB7xyXlMTTcZyO4fhymECy4oUKqzyasRoGuGyzkDg4DdrPZWc6Jw9199OBV4u6j8RX61eT5FaaRvhS3EJ9MyB4IOyDEhB7j_Ru8LJZas4AOzuRskdeGhSb5n5cJ90rmb9RGVgFS6hM97XsgQ", "name": "Coastal Conservation Association-Tx", "rating": 3, "id": "7258b034e119f31e82320bca6e72781ee9f79d75", "job_title": "Ts-Dudley-1", "place_id": "ChIJcekacM_GQIYRPzL13cgQrPk", "address": "6919 Portwest Dr #100, Houston, TX 77024, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.47039, 29.655454], "type": "Point"}, "properties": {"photos": [{"width": 5312, "height": 2988, "html_attributions": ["<a href=\"https://maps.google.com/maps/contrib/101184977609161362375/photos\">aug4</a>"], "photo_reference": "CoQBdwAAAMeBiHknWwRabFei8hAC-7vsHbyJ11KB40K4tyVS4uo1Qb2uat8wAsu1xI6scKM73ZUxV9RQc_GwGbbb_CllAjuk3Ry1MU39GJmE3ia8-f9Lc2tqGIyiSVispXK_Qtgs-HcyMyVhrnJYXWGw3Xn-czGJW9J_e-qMl5KiSB2cxBqAEhDWvO366-LIEit4pMW4l7QcGhRpoIhtiY9fBOWiEMb_4Z53r8o_cA"}], "types": ["park", "point_of_interest", "establishment"], "reference": "CmRRAAAAp6zFThXlybWfzcKw0CDzryyRDOVxqSY7Av_ftnIM8MqUg7jdLpFzQY_tIDxYXg2_aTow-Llry4_9ObYY7b3P_HFIImGHnspi9qma5-0S9cLudHKt4q-7ppudVAkos1zWEhBUnXMef4yjwZGfL5p_dqHqGhQPRf4uAdNaK62m5mLXYmU5cTNanw", "name": "Willow Waterhole Greenspace", "rating": 4.3, "id": "0127506e8071350c2d48f0ca56e939045297a0f4", "job_title": "Ts-Dudley-1", "place_id": "ChIJR6_2zTzqQIYRsA7wExgfDWs", "address": "S Willow Dr, Houston, TX 77035, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.4003322, 29.7388505], "type": "Point"}, "properties": {"photos": [{"width": 1136, "height": 640, "html_attributions": ["<a href=\"https://maps.google.com/maps/contrib/117056878997299689379/photos\">Marisol Brown</a>"], "photo_reference": "CoQBdwAAACQRTVvmMhkVIrUEZCvq_XqIbF9cPVotk6EnIiZFqjnGbO-a0UKYN5_Tfx7OYUk3B6AeK7UJLXziEFlIO3kC8zd25AjClxXPfxdz0CYbcDMM2LzZ8K4_ydhT7mJ6hAeaB8vf9HkTYrNv9REIvv6-orQ2KhnHzUhM1VHbL-mTT_jtEhBU9lGOd5LOHCFngsJjcN7rGhSJHRSmzy1np-XgZG2gx4XO0Wimmw"}], "types": ["point_of_interest", "establishment"], "reference": "CmRRAAAAuy5y0AvRyFY2tc4EImyOq1fjYtplnxdRV9OZfO8P0afItRAsLs_3wveS2dZORb1bCH0aPoRjA9fQnhRhYrQzxfTzy3gXA9vjfEx9oC93n3AHDnSaeLR16ELJM5uaExlAEhDckjecdxGIHUTNnota3VgUGhQIiZVZDcGKtuUSbIwjrJH-Eems4Q", "name": "Masters Fine Art Conservation", "rating": 5, "id": "a462c2eef4e22ea319485ae7b84f3d20756cbdd1", "job_title": "Ts-Dudley-1", "place_id": "ChIJp8u2bZvAQIYRbosnWz6cVmY", "address": "1612 W Alabama St, Houston, TX 77006, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.3876169, 29.794149], "type": "Point"}, "properties": {"photos": [], "types": ["art_gallery", "point_of_interest", "establishment"], "reference": "CmRRAAAA4bgAe-AMY7OwDVhJb5vdF-u3CU17CtACnp_47A90ywBF4kEnb1Dni6qXMiK688JS3gGCBnR0zltUtIBnTMawkCZlSvZMLgS-qEJZNpo4MQApW5auYgHF8EcEkN-aSH6qEhDhV6vmP73djzX_IOnHW6pWGhQJ7A3u_xQO3bnV66_OzsQRiesPeg", "name": "Whitten & Proctor Fine Art Conservation", "rating": "NA", "id": "883a8c5ef35ab28e1630235ad65a6b16506a67fa", "job_title": "Ts-Dudley-1", "place_id": "ChIJ8YuXE6K4QIYRn1SF1hazFEw", "address": "1236 Studewood St, Houston, TX 77008, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.3858767, 29.7300997], "type": "Point"}, "properties": {"photos": [], "types": ["point_of_interest", "establishment"], "reference": "CmRSAAAAkVRpMUeCYAKx0tS3th1c-C1nGLB1v9xqgD6nll1o-LktB4ka3KGBQmsBmFfqDC5eKTQpRuGDbQajcGAMaR1iNMiCJVjp3YD0VBny2c_liab_dd1Fba0UVPgZKy2dBsvbEhBKnGJrj0fVJbISMaKngLj5GhTB-sVTveG3f_26F0ePwlxyXCqFhQ", "name": "St Mark Fine Arts Conservation", "rating": 5, "id": "ea2d4bac6d74716b33f456dff3aae0cc0b43cca3", "job_title": "Ts-Dudley-1", "place_id": "ChIJKbDEoXm_QIYRcRFBlp0dE8A", "address": "4901 Main St, Houston, TX 77002, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.483218, 29.7482286], "type": "Point"}, "properties": {"photos": [], "types": ["point_of_interest", "establishment"], "reference": "CmRRAAAAfwA-u_CKSfNlmMkhoRwrdbIFawd3O4TNhq9c0XJGWt0Myn42n9ov-HLhJxgDe7d-Rb9mp9-QqNUnW2_VEBlJcrjJJx9wB-sMQpqEesNbmmBWh8h8DG18Pozxpuz5AuVfEhCoUtJgKOl73jQJbJ43oQKKGhQ-LDWGvhn70CvUr1bZFtdCb6cuYA", "name": "The Nature Conservancy", "rating": "NA", "id": "90af6fb9fb926dde9f7103577cebc4150bbb1dec", "job_title": "Ts-Dudley-1", "place_id": "ChIJq-m4EX3AQIYRJkn4Lhccp2E", "address": "1800 Augusta Dr #240, Houston, TX 77057, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.42318089999999, 29.7345943], "type": "Point"}, "properties": {"photos": [{"width": 750, "height": 437, "html_attributions": ["<a href=\"https://maps.google.com/maps/contrib/106788706324997826205/photos\">Erika</a>"], "photo_reference": "CoQBdwAAACiwgPP_BwoOScklG8QN6_z_wQC7XGKE0pGLhVo-NgjHzY7pV-LnuzrR4-kGScSC6Y65VaYtiLVvlZn41GmjD4eE6a9VN6N715gOwTjsberpKxnx3ecLMMjHUJKpgwZ66OfFi8VAfelU1rk27cXoYzGvYusYW_6ikGhjJCH6ZJxiEhAeo_3PY1vi1iZzEEtewVXpGhRo6jIAc34vOImv55OfZzGgazPYIQ"}], "types": ["point_of_interest", "establishment"], "reference": "CmRRAAAA1Y9sAiFlNYGS1xLmnBzEBlfeMhJ-nOPReJ2XZXhI7hWUmE8eVue0mKtMIK2rmVxsXPSUkh-hOY93W-A3i5EHkDp7II5Ba3EtkbXXvyNIwOagQO4zSPGY8pHvxuSIkKr5EhBQXQPRXpMHmQVn4PtP0IVQGhTpSQOQDDZYyCFkUG13q88NwjbjXA", "name": "Student Conservation Association", "rating": "NA", "id": "1c5ea7722fc0d99e9f7dfca55f5d9078224d51d3", "job_title": "Ts-Dudley-1", "place_id": "ChIJQcqBXfDAQIYRErawO-goGj4", "address": "2990 Richmond Ave Suite #400, Houston, TX 77098, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-96.038102, 30.055621], "type": "Point"}, "properties": {"photos": [{"width": 984, "height": 985, "html_attributions": ["<a href=\"https://maps.google.com/maps/contrib/110279808588468038448/photos\">Peckerwood Garden Conservation Foundation</a>"], "photo_reference": "CoQBdwAAAMkCYMACF-HeQZU0_Yba4ZgH7O2597cw02mOq7P9Nda9tckeuU2mRg9rYlIPamXoEYsGCfi1SgwyoNUTx7KuoMpSNLrUBz3e7ZAQBeZjw1xHi5gxBSi0l7IqWVFp4xw4ENVTy3DA_XV1Y0WMFt4gy95El43j9HJGGJwUC6crumIZEhCzE0nGxGRxuAMpV_AwNXOJGhS5np56ILurgYVNPjM-GtToYj6_UQ"}], "types": ["park", "point_of_interest", "establishment"], "reference": "CmRRAAAARWNithrVKgCa3D7kOHjqf8D99jV8kIwOxC9h2L2jjgRYDm1LtQRCXWocLDCKqLIdmo1A3QJtik7Xk_k9O6FHpe1i30GxxsfgV2gCSffbwLWT3bLwwyvczctsy5usHKGIEhAsl3KQ23k6DjPw2X-FZ2jGGhTgKLcX9TqQVirwa2TTlH16fGpxyg", "name": "Peckerwood Garden Conservation Foundation", "rating": "NA", "id": "e618a4c618cd67ce4f5fdc165f640220ab3b53b2", "job_title": "Ts-Dudley-1", "place_id": "ChIJmUR7pvHKRoYRIIl0o73bPGE", "address": "20559 Fm 359 Rd, Pine Island, TX 77445, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.64386449999999, 29.7515036], "type": "Point"}, "properties": {"photos": [], "types": ["point_of_interest", "establishment"], "reference": "CmRRAAAAG8LZccRfkaxaSFw0gljOi6i0zl39sp_dUw5P4k-LouhjdHoHk5kxZXZzByhiaUwv_b-Zyyfn7QiRGZWsj63p4YMAcjMeBzbAnu6MTo-vq5fGbb9q152Y3sa2oGOyTrU-EhAgrRW4IkurnTyEnqyjOB7MGhRokAJVw7ITp5UHtQmWbpor_4SEeA", "name": "H2O Conservation Technology", "rating": "NA", "id": "30c07988ef8dfc62dac712b9d587daa4a36f2539", "job_title": "Ts-Dudley-1", "place_id": "ChIJIWZRKeHKQIYRXxta3wOMGGc", "address": "1725 Hwy 6, Houston, TX 77077, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.5705632, 29.7714443], "type": "Point"}, "properties": {"photos": [{"width": 3024, "height": 4032, "html_attributions": ["<a href=\"https://maps.google.com/maps/contrib/108143329814504597326/photos\">State from Jake farm</a>"], "photo_reference": "CoQBdwAAAKxS4mSDU9qtRNJeIzFcmwgCoiZbMMvYak0tcHgbqpQa4LRw_5IggJuCwi1-n9gvt0v6SQrC9xJnmIKHgUwFQhGI9gAtxlvMBI8MoShrWsUIhMJw-tePQmz5mDNoOCND2Nuq5xawCsa4ncc1x696ugThbrTA_-3EWK_lXX5SmmtIEhDinyW7U1B2tBVEAfjbRTt-GhSmbEVxo-NTNUBd_5kKCV1ergRIlw"}], "types": ["park", "point_of_interest", "establishment"], "reference": "CmRSAAAAu9nb66hYVfK3sO3KwoWp4v2Y-A34QxKA8X4yuJZFht8NYZYC-ALGMmA313vfIiCmwWJIzJUgn2CYIqstARwrj9zoGxzgnLzmW2OkGeHgv05-Rdl5wr_CSNtbtru_lKruEhBA3wEYRPh91ajQynDrj_hHGhTbl9Bxx1xt2AfwE0tBTCUbjPaRvg", "name": "Houston Audubon Society", "rating": 5, "id": "050a5458d86bdd1cee7b09678bd6256d0a20a73e", "job_title": "Ts-Dudley-1", "place_id": "ChIJlQOxwVDbQIYR2uX_TZl0TYc", "address": "440 Wilchester Blvd, Houston, TX 77079, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.56820189999999, 29.770778], "type": "Point"}, "properties": {"photos": [{"width": 1800, "height": 1200, "html_attributions": ["<a href=\"https://maps.google.com/maps/contrib/108765250995932379967/photos\">Audubon Docent Guild</a>"], "photo_reference": "CoQBdwAAABPi05dsBuQrjWEJrT3ayooixePekssImM29u_8S5kzSMR4f456HxRfrsBdqGV5CCJdRXHeclXLBI-dPsD61plqwpBunvPGGimR0FmYz_8ntSNc2enymbG-RCbDGl7ypqdrPoDWq2PbNrfc-uhJf07UEjTzj6HbL-K6gCtbwWKseEhCknIxHpAft7-mYyd-5zlIQGhRJ3UzWSbBNvUn6tflCy9rVrJLEVw"}], "types": ["park", "point_of_interest", "establishment"], "reference": "CmRSAAAA6c_HgyR8kQzlSxTvndKc3MrX37A8J2hd93gKgpaoXDQCh24ubsat86PbMJxMwMP9BfXbcvp6SGmBj66WnOKBGhzeRqO3D5OmHpPxKYxzXZlKGfm2CDCfUtUluENH5LbiEhDYDWL7afNqj0ETisCoBT3TGhRrsRC84naPgiNr-hsizZeg6FHzqw", "name": "Audubon Docent Guild", "rating": 5, "id": "7ddd5daf76cc4979e2ba6b062322d1c77d5d1c07", "job_title": "Ts-Dudley-1", "place_id": "ChIJI9XyNFHbQIYRtwHb8EtTpeU", "address": "440 Wilchester Blvd, Houston, TX 77079, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.44932349999999, 29.7803218], "type": "Point"}, "properties": {"photos": [], "types": ["point_of_interest", "establishment"], "reference": "CmRSAAAAs9KqADzKGEDPFoY_ZUyi-ynzvwSH6Jv1dQu6-is657RlZ-Ojbw4B5LlDaj6NADDlElw8qyI3fTOrFfUM5DmrTAEcqL0Yr_Q2gXe8BOJ7GGjoACkdj6Px9XvDz6SVGa4vEhCyijJy5uRXtLXoO4umC7XxGhTo9INiSsey3X3rRW0_wPv1zm-mRA", "name": "Coastal Conservation Association-Tx", "rating": 3, "id": "7258b034e119f31e82320bca6e72781ee9f79d75", "job_title": "JPMorgan-Chase", "place_id": "ChIJcekacM_GQIYRPzL13cgQrPk", "address": "6919 Portwest Dr #100, Houston, TX 77024, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.47039, 29.655454], "type": "Point"}, "properties": {"photos": [{"width": 5312, "height": 2988, "html_attributions": ["<a href=\"https://maps.google.com/maps/contrib/101184977609161362375/photos\">aug4</a>"], "photo_reference": "CoQBdwAAAKMkipf5OjisTKEIMs76PsU3qTCCTpUmkCmyVU_v0CG2cKQs-hsjrXRkqJm030PbgMznr_AWFvb3BgjoNQzVff-pw6lVe1IqSWJC360ZCzhJo_uJimPm4dDVQ-3-uf7k_09ngVTl-PmrqwwO--kK4jDCShPT2MDcWk_HnOV8F_h9EhDyp8Fiwn206g42yudwUKrYGhSouH976Q6I9MkEqe3uVaoH_sB6qw"}], "types": ["park", "point_of_interest", "establishment"], "reference": "CmRRAAAAbJDSCF8PkduLdWqqJUvzMb1QXvqKTuRwTyhBuu-TaI3N7K2Q34-JY5HqX9WP1SvKHZSSX5ThwRsugGp9KyPGB0kGKgMKxQ1gIJRYMAtNHnXe3UJlzn0bcJTklJtgSC12EhDihGnWQ_NLZmPAmZK0qaOjGhTynlyh_sKmbkEg1UHyy33YS_XemQ", "name": "Willow Waterhole Greenspace", "rating": 4.3, "id": "0127506e8071350c2d48f0ca56e939045297a0f4", "job_title": "JPMorgan-Chase", "place_id": "ChIJR6_2zTzqQIYRsA7wExgfDWs", "address": "S Willow Dr, Houston, TX 77035, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.4003322, 29.7388505], "type": "Point"}, "properties": {"photos": [{"width": 1136, "height": 640, "html_attributions": ["<a href=\"https://maps.google.com/maps/contrib/117056878997299689379/photos\">Marisol Brown</a>"], "photo_reference": "CoQBdwAAAPkGTTPFA5M1zRT_vPIcsBTGpdyWGaDEakLdKS_pNSU3rswwovty0bH8HQgxJUMyK4hNwfwWfmjxxyZPgT3LtqSyOeqslcQM5gZHqDYSlQiqkHGaTew4j_d618DU7FDvSyQM5eiuORbknHvPr7rGNNRrw88SHrsIark4rNE-3uTCEhCRx3tvxRXK5FvyUBlsNd60GhRNRIdZwE__E1HV0aw5IWnSLrBGog"}], "types": ["point_of_interest", "establishment"], "reference": "CmRRAAAANfo7PHsDhudAg99vm5vmiF3rw1teyll_l7ZQCy0SH6LnsQRYLMcjV-Xphr65UsPResBbGL4IBu9EDuEHaWhsMt_X2EiZ3JieHPAT6Q7fUH6a5g6UqsNdtBauHTJs5vEzEhASSalo19qe17eqVa_IlU11GhQ3kV1AnWpV7smMbFlLfd6NZa1rPg", "name": "Masters Fine Art Conservation", "rating": 5, "id": "a462c2eef4e22ea319485ae7b84f3d20756cbdd1", "job_title": "JPMorgan-Chase", "place_id": "ChIJp8u2bZvAQIYRbosnWz6cVmY", "address": "1612 W Alabama St, Houston, TX 77006, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.3876169, 29.794149], "type": "Point"}, "properties": {"photos": [], "types": ["art_gallery", "point_of_interest", "establishment"], "reference": "CmRRAAAAQmSUTL0Wh4Qs4Td3EFvPUScjacxZzhn42nAwGVMeya7qkItYpVi8S0zfQ7F7hOsT0AP4ZL04-kHECu9eo4NqYDTtEckN-Ozzun6e8ZrVOD1yuO4uCbaRt7ljiFj6YbSjEhAlsf96t7E1iPeO6E68bMUVGhTA-UdR0bnRKZ4lT4Ab-lKLPFKm3w", "name": "Whitten & Proctor Fine Art Conservation", "rating": "NA", "id": "883a8c5ef35ab28e1630235ad65a6b16506a67fa", "job_title": "JPMorgan-Chase", "place_id": "ChIJ8YuXE6K4QIYRn1SF1hazFEw", "address": "1236 Studewood St, Houston, TX 77008, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.3858767, 29.7300997], "type": "Point"}, "properties": {"photos": [], "types": ["point_of_interest", "establishment"], "reference": "CmRSAAAAgO8a9w0b5xEqclMtxZXBS3sGeJCKF4-CtvNlp6rLXY0uY9G6norQBcQQwgT0zsaMP08b4GX2wwzGLZ3NULTyxTC0-khV6W3-dEedmn3p-YxuoSQel2B8xtDYRd7IJFpZEhAdVG4FhJoOSzoJRm5-8KBUGhQ63yeUvTZ-zpsj6x2dYTSerid84g", "name": "St Mark Fine Arts Conservation", "rating": 5, "id": "ea2d4bac6d74716b33f456dff3aae0cc0b43cca3", "job_title": "JPMorgan-Chase", "place_id": "ChIJKbDEoXm_QIYRcRFBlp0dE8A", "address": "4901 Main St, Houston, TX 77002, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.483218, 29.7482286], "type": "Point"}, "properties": {"photos": [], "types": ["point_of_interest", "establishment"], "reference": "CmRRAAAAhe9jN4UE6DWGnfYvBzbjXy7FIqPua1aBHCDZ3SKsC-0rTUNacrRietbsuu-4JAYaYrfm9fhf3e-hDVZtUEstUfmLq4PbWWapvkdb0zkX8uc8J5IyX42g6yvdBwLE2RefEhA2St05FgQLLuKzKm5qwd_GGhSKcqrhLXsWOsuUmi5RP9zXPxu97g", "name": "The Nature Conservancy", "rating": "NA", "id": "90af6fb9fb926dde9f7103577cebc4150bbb1dec", "job_title": "JPMorgan-Chase", "place_id": "ChIJq-m4EX3AQIYRJkn4Lhccp2E", "address": "1800 Augusta Dr #240, Houston, TX 77057, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.42318089999999, 29.7345943], "type": "Point"}, "properties": {"photos": [{"width": 750, "height": 437, "html_attributions": ["<a href=\"https://maps.google.com/maps/contrib/106788706324997826205/photos\">Erika</a>"], "photo_reference": "CoQBdwAAAKCVgypMdbSCIOJdiZ43-cakamVsjCqsOcMQn5bU2_CXW6oY0LTNuTidr6UH3epdETOZZpb9si7D--N8QgZYIirrYxkkJvYSXQzX_0SHAIjIqxZQIKO6qTpYnoKaOvj_UhGR2Yhq9bFjc96t8XQddNVQmAXzO0tb9tE8KAOdUrYtEhCgxEhf4JhXirIkNZoPqeVnGhTqKcFI6wNotkTfHdodgihBsJ4mCg"}], "types": ["point_of_interest", "establishment"], "reference": "CmRRAAAA0Sp4QH9O2rxyMnFCAuwsTt-klbqtZqv4GxmfEGGVy-ol3JRJxrOT8Kk4zqS-I0I5iRZe3WFWXfNLuq1TSQWgh7UMPb9_F-u_8bAsLgHuLUBlbZNNKAUPyq2D2tw7x__zEhAgVGOH9CnxzVgeeWRdeXKZGhTF91rwandWR4vs7FE3esTaWuLXhw", "name": "Student Conservation Association", "rating": "NA", "id": "1c5ea7722fc0d99e9f7dfca55f5d9078224d51d3", "job_title": "JPMorgan-Chase", "place_id": "ChIJQcqBXfDAQIYRErawO-goGj4", "address": "2990 Richmond Ave Suite #400, Houston, TX 77098, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-96.038102, 30.055621], "type": "Point"}, "properties": {"photos": [{"width": 984, "height": 985, "html_attributions": ["<a href=\"https://maps.google.com/maps/contrib/110279808588468038448/photos\">Peckerwood Garden Conservation Foundation</a>"], "photo_reference": "CoQBdwAAAAjl44SSX4GROhq6um33bYUaDnYEyhFoaezggXMTBXojlLFN3HcXh_lbmnPghiAR3V6eRFY37GJlwvJJvL6XuhNQeyh6Q5VogkOcC_LtX-5Vq_k0aURv3LqxIH-s_bfmHxiYNG3Vk7dJ9BnGEDymhTMxoUka2eCJWBcf8v5JjEBzEhC041MHzUNroC8xw8gfS7EwGhTT3Kpkm74DdaG3ys5tdd5hRB6F7Q"}], "types": ["park", "point_of_interest", "establishment"], "reference": "CmRRAAAA9x0cSBTHRSd6u-M_1sAtHB1Fv1wF9auHywkYrn3yua5JPyn-YEfw_aE2TFrkWw-1WjUUfTLmEs-yEKVGPkv-nyX80jkbJlL3bPX2NLCfUDzv6GYJGjPp1wwBovf-Qk94EhBCxfMI6r3gJbhdky2tZc9dGhTXVaF-HJGoNE6dEjr3HR9EGdQN-w", "name": "Peckerwood Garden Conservation Foundation", "rating": "NA", "id": "e618a4c618cd67ce4f5fdc165f640220ab3b53b2", "job_title": "JPMorgan-Chase", "place_id": "ChIJmUR7pvHKRoYRIIl0o73bPGE", "address": "20559 Fm 359 Rd, Pine Island, TX 77445, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.64386449999999, 29.7515036], "type": "Point"}, "properties": {"photos": [], "types": ["point_of_interest", "establishment"], "reference": "CmRRAAAAPI12TcCGdyUhaX1QhI3lXrB6p-yRtwftJPz8dUqxVKWXVg6IviK80oktivlhr_US0Mi-ar9G3_UHoTxiCRMRgTEBU9wnJOhFrVQUSnMOHTHVszinqU9rAEULh-UNoRLxEhBq_wtAOp8QgWqQFQLK7YCQGhQuSoWMNGQgfmUjPLHQ86S0G32IbQ", "name": "H2O Conservation Technology", "rating": "NA", "id": "30c07988ef8dfc62dac712b9d587daa4a36f2539", "job_title": "JPMorgan-Chase", "place_id": "ChIJIWZRKeHKQIYRXxta3wOMGGc", "address": "1725 Hwy 6, Houston, TX 77077, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.5705632, 29.7714443], "type": "Point"}, "properties": {"photos": [{"width": 3024, "height": 4032, "html_attributions": ["<a href=\"https://maps.google.com/maps/contrib/108143329814504597326/photos\">State from Jake farm</a>"], "photo_reference": "CoQBdwAAAHLsxC9usXzeeVCmwQd0gSYW2gr9BT5ymXvYc1TruhLcMlnpxTKWj2HD6nLby98PIFDQTEXRrJ_IT0T80ORuAtFe5sLSHMNXWJh2ZaE_2qgSUvqstShkN57Zi3asZOF0AH8o5r7ePGBBIrnvS4QhMmznBLi5T9fFUmlqEs5ayrTCEhAjLWxXIMHIkAEh1NYPAaquGhSvwIveTqveCAh9_LZMGvqo-xUZtA"}], "types": ["park", "point_of_interest", "establishment"], "reference": "CmRSAAAAjT08tl7M50FFHn15kgkIu0EhePdMdWhOM4oL_DjHPffzoQFZ-_5AxXZJVLx-289GJ0EBpEHDHddvHQASDgyzGIDqgDFKou7SSFD30Z8tN6lj3Ain8ZT1T1F85vMtilmXEhAGrVW_HqCFnPf-mxOC3e1uGhQGtOw3C3s4o7crBTFmMfhz80f4GQ", "name": "Houston Audubon Society", "rating": 5, "id": "050a5458d86bdd1cee7b09678bd6256d0a20a73e", "job_title": "JPMorgan-Chase", "place_id": "ChIJlQOxwVDbQIYR2uX_TZl0TYc", "address": "440 Wilchester Blvd, Houston, TX 77079, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.56820189999999, 29.770778], "type": "Point"}, "properties": {"photos": [{"width": 1800, "height": 1200, "html_attributions": ["<a href=\"https://maps.google.com/maps/contrib/108765250995932379967/photos\">Audubon Docent Guild</a>"], "photo_reference": "CoQBdwAAAM6x89OHRsq3y-5BPksa4BdAhQE0YmL3cfXP5ev2faPKUx0nJHAN73nZ7RtPAizNnMszxEJtMQ6JJ_uXciSPNlimStY5C4AM_bW9tyE2FvUCulbAcrvst1y2SOnsGTRAbYT7aFp13i2bJQ3hk7E3bxyv3HebAaBbOoh8Ek33nvbnEhAQ9GRkw2m5YSsEUJSQ47_mGhQIEZDQEmW6LciXbStk2fxnqPd5cQ"}], "types": ["park", "point_of_interest", "establishment"], "reference": "CmRSAAAAIq9mb9lG2sTnFYardAkbVnmIleg6BEsVaWJWxqgBKmDW2GnffwDZaazLa2Ix0Nmq9jGH0AebmGlADaqjZ8E1IjKaE0flWtCE9LpKbO3ap7qfUA9K9o8ZYqAvJRRFxuz5EhBF629ZSxD6qP-xJckrsfafGhTptciZ3UbfcvEkFwp65g1Je6Uy2w", "name": "Audubon Docent Guild", "rating": 5, "id": "7ddd5daf76cc4979e2ba6b062322d1c77d5d1c07", "job_title": "JPMorgan-Chase", "place_id": "ChIJI9XyNFHbQIYRtwHb8EtTpeU", "address": "440 Wilchester Blvd, Houston, TX 77079, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.44932349999999, 29.7803218], "type": "Point"}, "properties": {"photos": [], "types": ["point_of_interest", "establishment"], "reference": "CmRSAAAAVu4xxJGBvSiS_d7mSiVbVExaJD1lnH_FWf-O37tLupBLOoMGkKYB3piZJY4J1sw8f7KzC7t3cu6pXabDy_AVxR7x7i3K4IzsyWS9_1coaLhPqtpNyT5PogO2SP_ucpmVEhDdjdi1uf2pyz8wl9_8bj5fGhTzPIT8OJ5jzv9mtyxVY9D3Gyuc_A", "name": "Coastal Conservation Association-Tx", "rating": 3, "id": "7258b034e119f31e82320bca6e72781ee9f79d75", "job_title": "Macy's", "place_id": "ChIJcekacM_GQIYRPzL13cgQrPk", "address": "6919 Portwest Dr #100, Houston, TX 77024, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.47039, 29.655454], "type": "Point"}, "properties": {"photos": [{"width": 5312, "height": 2988, "html_attributions": ["<a href=\"https://maps.google.com/maps/contrib/101184977609161362375/photos\">aug4</a>"], "photo_reference": "CoQBdwAAANFBgHrRrktP2ZPFk81GLAq7td-UJfcLExCNOzbdVRftTIGzkzbmOLYS3k3xYqgRCBhs6h5ceWY2tLEAuSxnJs6Y9VPaDXgZL2YpnL6I71KzoqVGIPsCP6T9D3LVOi4iAkHz345vAc-bC4YS8x7oq5SuVYKqSBQRZxgrtEMTOkJvEhD65HlY7eKtIIizfWgzKAegGhRfW4J_1uzTpz1hs482v7QViMA9Mw"}], "types": ["park", "point_of_interest", "establishment"], "reference": "CmRRAAAAqBDSNuWaU_MWAOOTVu00GSTLHVoVbhezymFWN8BzDUpzBUt-dUeSOW_tB11RmwJUsGDIRD_wXVp-UP5dTQbuOjKHyt0ftrP1iXIFIHfsIVU2ovWLLPKKOEpmuF7qrxCCEhBeqBu1ryBj8hT9PSDkkquvGhQbVmokZoTiKdx5QMz_3rtCqbD6Bg", "name": "Willow Waterhole Greenspace", "rating": 4.3, "id": "0127506e8071350c2d48f0ca56e939045297a0f4", "job_title": "Macy's", "place_id": "ChIJR6_2zTzqQIYRsA7wExgfDWs", "address": "S Willow Dr, Houston, TX 77035, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.4003322, 29.7388505], "type": "Point"}, "properties": {"photos": [{"width": 1136, "height": 640, "html_attributions": ["<a href=\"https://maps.google.com/maps/contrib/117056878997299689379/photos\">Marisol Brown</a>"], "photo_reference": "CoQBdwAAAOtK5oLXI3KSgcrx2fbgaUWr1a9TIazdPqu6stHtD-guxkx39c7-3r7KkcvWdL3VWsiPs7efI2diJM1sKFMCcP4vaW_1CTT2sX6p3feloef2RrqtAo7bEEP0ujxo4TTlt0Ozq6sIYjjQZzcKjIyGL7emFojbvc-ZD9ob_ClnYBLEEhDSNwuBO0NJUECfepNxjfj4GhTsvhBv9KnF2L24ENRXyoaAcSlAKQ"}], "types": ["point_of_interest", "establishment"], "reference": "CmRRAAAATXD41oWfm9NiCkyxOZsX4Y7-obrTNF8ss3z5EG-vRaKnf4K2z4xc6YLClybXIEA7YCqsFYr3pOvXM3FYqpJnc2y6B6NuZoGnmrFoxxFr4uthj98XZvg_eHZU0MUugwSdEhClPcEu6XbwtX_3vGlSKW7JGhQWrQNEMLzDkmrp7LprbuSoXCBVJQ", "name": "Masters Fine Art Conservation", "rating": 5, "id": "a462c2eef4e22ea319485ae7b84f3d20756cbdd1", "job_title": "Macy's", "place_id": "ChIJp8u2bZvAQIYRbosnWz6cVmY", "address": "1612 W Alabama St, Houston, TX 77006, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.3876169, 29.794149], "type": "Point"}, "properties": {"photos": [], "types": ["art_gallery", "point_of_interest", "establishment"], "reference": "CmRRAAAAFrKy_VCUllgKkNTWkXVGDYwMWiskMI7rl3S9ewiQtLBD_1MEsvZl-bF17SLZLwreMRKVOu-Xnr1PPXcfjZPBlaVCcdPm1rekstS5kxkL953gp1n4DuFVC-MzY8-t_KdLEhDrFqK_lCewzh8RrfBQqYhQGhQCzEy7ntq1WtCFlqq_yXy66Uhkhw", "name": "Whitten & Proctor Fine Art Conservation", "rating": "NA", "id": "883a8c5ef35ab28e1630235ad65a6b16506a67fa", "job_title": "Macy's", "place_id": "ChIJ8YuXE6K4QIYRn1SF1hazFEw", "address": "1236 Studewood St, Houston, TX 77008, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.3858767, 29.7300997], "type": "Point"}, "properties": {"photos": [], "types": ["point_of_interest", "establishment"], "reference": "CmRSAAAAhebaPfpt8b883HqQYBAJJUlRsweCEoYccm6EnXL4_l1FnrzTJihPsVbZbmDU17_gITLDALIV93P_yODfN_mYSSYZgnhu_xP685D5eaqAs8T3DEQSdJOBgAUKs3Z1R-XqEhDg2H54ithsf_b-bUAr3eUOGhSSfRVrru3sAI-pR5auFrxzp10toQ", "name": "St Mark Fine Arts Conservation", "rating": 5, "id": "ea2d4bac6d74716b33f456dff3aae0cc0b43cca3", "job_title": "Macy's", "place_id": "ChIJKbDEoXm_QIYRcRFBlp0dE8A", "address": "4901 Main St, Houston, TX 77002, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.483218, 29.7482286], "type": "Point"}, "properties": {"photos": [], "types": ["point_of_interest", "establishment"], "reference": "CmRRAAAA9p5raZTFwszeqYaHcsS5BtU2ho12L9EKgeh5Gl_xW52lrCUeiAxCvNTpKFd34FiOF3soT16aWRU_N8P3FcWE0PvO5VZy6XUxBdhLCCrgOv6QSmPRbOqmsZo1Hn_XryEOEhAvu4RISNVRtObIQV9AshnTGhQ2ZLrkyTZugmdU_Wt7QoBridxmsA", "name": "The Nature Conservancy", "rating": "NA", "id": "90af6fb9fb926dde9f7103577cebc4150bbb1dec", "job_title": "Macy's", "place_id": "ChIJq-m4EX3AQIYRJkn4Lhccp2E", "address": "1800 Augusta Dr #240, Houston, TX 77057, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.42318089999999, 29.7345943], "type": "Point"}, "properties": {"photos": [{"width": 750, "height": 437, "html_attributions": ["<a href=\"https://maps.google.com/maps/contrib/106788706324997826205/photos\">Erika</a>"], "photo_reference": "CoQBdwAAAMPbcJsdXhiEzPkxyKwKTxTiAuWy20ZjoCWB1QKOysERDPYUVNFjzYB0vEJSUwWNS-tIl6neq3_kL3dt06vtlzW_pcNg7nIdO6Ze54Ex5cSCBWT_n9Litn1jjP4z-pPuQjWHmTZgdIM2gdvfd-aIK0OHX86dvM6lBgsTgKVgeqsrEhAYUYL7c9c63_eh_2ymYwjBGhSNBS_2d1duvQCPptIOSPb8Th2XSw"}], "types": ["point_of_interest", "establishment"], "reference": "CmRRAAAAM8iO-AS0nNjuWsZ8lhKsxis1xmkk-kq7vADIkrfPgfHwTS3EcFBjwlWgWjdAg5sVy_0Y3PXisVKlBIf3FZFjyJ1ft-HQcw4Q5Hr8Oa-mpXkngnE5tz4W_MLgoNm7WnvREhC4vPisGuGv99ACi4OeQZ6eGhQfSWZ-juGpCR_z4o87OrM2AP13aw", "name": "Student Conservation Association", "rating": "NA", "id": "1c5ea7722fc0d99e9f7dfca55f5d9078224d51d3", "job_title": "Macy's", "place_id": "ChIJQcqBXfDAQIYRErawO-goGj4", "address": "2990 Richmond Ave Suite #400, Houston, TX 77098, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-96.038102, 30.055621], "type": "Point"}, "properties": {"photos": [{"width": 984, "height": 985, "html_attributions": ["<a href=\"https://maps.google.com/maps/contrib/110279808588468038448/photos\">Peckerwood Garden Conservation Foundation</a>"], "photo_reference": "CoQBdwAAAALETdVl_TZJbbI9jJkx1e6nVOHk8GcTY2QlevBcKkaH9FvSsbaIQ5kCjI6yEBWk2v-I_klButF-idSbQBTh8SaHvp7fwsj7mxuu5DJi-byzTw5Cw6WyEbIl7Jz1_mvhkyY8mbXZXitAu-Ffte1_YplcBdiVGm572g30hVSFMB-gEhCEZRTTJSMuU2l_HmjEnypcGhSlyD-cSEAl4l_hKCQrMXDT3wxnUw"}], "types": ["park", "point_of_interest", "establishment"], "reference": "CmRRAAAA2m_NbqFffjRSs4U6rlag13QNA8fnomWQ8yp2s2XLip4alQMkQWq2JN9svRdeBIzGEqxjkm_fjihA-vRQb7rmpBjbQ6z-ZZ06w4ye8XscNIoCxwgsH39ylN-goZPTKtfDEhAv1_-THXqz7lFdVtUFw0IvGhQ5-oqEwMr9RzjcEy4CBtdok23Hzw", "name": "Peckerwood Garden Conservation Foundation", "rating": "NA", "id": "e618a4c618cd67ce4f5fdc165f640220ab3b53b2", "job_title": "Macy's", "place_id": "ChIJmUR7pvHKRoYRIIl0o73bPGE", "address": "20559 Fm 359 Rd, Pine Island, TX 77445, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.64386449999999, 29.7515036], "type": "Point"}, "properties": {"photos": [], "types": ["point_of_interest", "establishment"], "reference": "CmRRAAAAPoo39XiBKKRF0Q9Q_miQaosl74ht89mUtaoCS3Vd0PIM91jC3JTWlASvPNPb2c4hxzyFjxxGHkmeoH4XdEJV_KYlMCpbawL4XFKCaBlGph4WxVDBB2HfbUaeorw8meSZEhANsY4tKX9IwzbWp1qHRUvkGhQZbbe0h_Vy4F1kmt2eRwMfX__zFQ", "name": "H2O Conservation Technology", "rating": "NA", "id": "30c07988ef8dfc62dac712b9d587daa4a36f2539", "job_title": "Macy's", "place_id": "ChIJIWZRKeHKQIYRXxta3wOMGGc", "address": "1725 Hwy 6, Houston, TX 77077, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.5705632, 29.7714443], "type": "Point"}, "properties": {"photos": [{"width": 3024, "height": 4032, "html_attributions": ["<a href=\"https://maps.google.com/maps/contrib/108143329814504597326/photos\">State from Jake farm</a>"], "photo_reference": "CoQBdwAAAOI3QqvtxFJbQGZuiQ4qA6H9abOi49EEmoBuusreAHLE9kgI0HbNCbW1WEVyXz1PgCqXuF-Heg29KPl6eyjbEn8vAWl8QmARhY00ynYXz2BBiFPp5i_XWucxUGFb42QD1eZA6ULOy47l1mAaZPTIRqB_t_PAjF_FfXdRzg1hR_d1EhC5WzC5XP4va8ftAaqN6YyrGhT1VwO0jblWfd-oOssmF3rSk-j7Sg"}], "types": ["park", "point_of_interest", "establishment"], "reference": "CmRSAAAAe5zXPx998eerGR8Gsltprho6HAcWb1tcEoH_Bob6w0EB_rmAfeBHkIi3jxwrXXlIm9YgIyRjnxVZKyo6V655y4lxfFxeq5qrAU9sJUDYRkRgjJyqejGjW22ZNUb5m35mEhAn4gi2_Se5rXXG7QmnjKl-GhQG8Np5eKj04qNQaFcHmFe2A3eLrA", "name": "Houston Audubon Society", "rating": 5, "id": "050a5458d86bdd1cee7b09678bd6256d0a20a73e", "job_title": "Macy's", "place_id": "ChIJlQOxwVDbQIYR2uX_TZl0TYc", "address": "440 Wilchester Blvd, Houston, TX 77079, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.56820189999999, 29.770778], "type": "Point"}, "properties": {"photos": [{"width": 1800, "height": 1200, "html_attributions": ["<a href=\"https://maps.google.com/maps/contrib/108765250995932379967/photos\">Audubon Docent Guild</a>"], "photo_reference": "CoQBdwAAAB8h_xSKQ5zkLfdwVyXv7AlRUFtsLDks_5Nx5fZNiZihQf7DDJcTtT07YmQjBNS93pf5ZZln4PgdoHskNc6TIgpJJK0fN4VBtAfnDzgnqywqCE9RCboJjt8EsycrocdCTXPSh6qqyS2jKbz69aFMb7NWuQmx46uG7HiuKWbSdZ6pEhBcJMGHvhMWxqKCzD6Zbyn6GhQUxIy9TBUuYxKYGdPkefQ84AS1ug"}], "types": ["park", "point_of_interest", "establishment"], "reference": "CmRSAAAAiuv8hcSWuB0hIYcW4k4VdxW1Niss9eexAUZhAH8JCT1MKt70iDxFRMFfdBFD44shF9m7cp_BuA6pWcr-HSOSTCD6kwBCIhQ5NdPhjIMLnD-CYNugbQnUTANoI-2i_ApFEhAD30EX5PMeJyL7_8bkXuJuGhS1qhAMCC_IVVjGcpKtI7RbtlBMAg", "name": "Audubon Docent Guild", "rating": 5, "id": "7ddd5daf76cc4979e2ba6b062322d1c77d5d1c07", "job_title": "Macy's", "place_id": "ChIJI9XyNFHbQIYRtwHb8EtTpeU", "address": "440 Wilchester Blvd, Houston, TX 77079, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.44932349999999, 29.7803218], "type": "Point"}, "properties": {"photos": [], "types": ["point_of_interest", "establishment"], "reference": "CmRSAAAAI-RUAxVsy1Zi4B742n9nLgIeaVqHgaG5YY0b3yjh2kZgWbjUwCzAD2nUZv2dDIAhjZkU0OsoLNzOrpBAAn13lKKojv3H6j4kGg9KifnTA2NlpQQOM14nWan7ZEEhotzPEhA7pOvEnr_opm0rf3T8jy66GhRdO--xXA_AHylZ_r6dN6ah2OU2Ig", "name": "Coastal Conservation Association-Tx", "rating": 3, "id": "7258b034e119f31e82320bca6e72781ee9f79d75", "job_title": "P%26M-Onshore", "place_id": "ChIJcekacM_GQIYRPzL13cgQrPk", "address": "6919 Portwest Dr #100, Houston, TX 77024, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.47039, 29.655454], "type": "Point"}, "properties": {"photos": [{"width": 5312, "height": 2988, "html_attributions": ["<a href=\"https://maps.google.com/maps/contrib/101184977609161362375/photos\">aug4</a>"], "photo_reference": "CoQBdwAAAIHZcjoVomYl8YvliFxrYYsVRrHj9Od7znZ5YHuQAQwN6Ryrdg6SJsMNSI4kkmijBJM3otrniNIIPA8E1eDhJ1BDVoAzf_uNMOczFHoj4ohRdOFVDbxEJ1HftPDO5xZXBCyVC2jFUscrgUQrusdRZ67zy6zEr1mcJyinP8m-_wSHEhBhRcaz7ig3olkgM2BbKkIQGhRF1dFML51lPqY61kuZ7EEqihwEuQ"}], "types": ["park", "point_of_interest", "establishment"], "reference": "CmRRAAAAviU_TuRk1UX0-xAOdUeN4ZSc6ToZbMCEoHiqHFsIqxiXvMHbtWcVsRoflcfx0-Nw3F-HetDE709asoHEqdJMGMHcI1beyeh7tOziJRYSroh6C0z-Nz3DirYaNv9p8WLmEhBi6LAsXumx80lZMtMslUDbGhTofHA7ZUWpkAMgKA93vOMiHIOLKw", "name": "Willow Waterhole Greenspace", "rating": 4.3, "id": "0127506e8071350c2d48f0ca56e939045297a0f4", "job_title": "P%26M-Onshore", "place_id": "ChIJR6_2zTzqQIYRsA7wExgfDWs", "address": "S Willow Dr, Houston, TX 77035, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.4003322, 29.7388505], "type": "Point"}, "properties": {"photos": [{"width": 1136, "height": 640, "html_attributions": ["<a href=\"https://maps.google.com/maps/contrib/117056878997299689379/photos\">Marisol Brown</a>"], "photo_reference": "CoQBdwAAADWIueAuQT8UWFnuHAA6CUPEwYbAxX0wwxjR2blUydrVcdvzDY0-2zm3kC7XrnG6CZAN0yZfBTITHrKxL3_QLRGs1IpllGGHJ9ccfNigZw3QMmzVCCm67cUIFu746SLXkHkAz2Ffo2oMSns36HDqBp_jkwiIIi5XuutPmkGmFJ8PEhBVp65Nl5fd_gwoLovgeBhyGhSQeA2E3tKSPydRyRDrm9J8UV_S2Q"}], "types": ["point_of_interest", "establishment"], "reference": "CmRRAAAAcIkT2ahYDvGX3w84Xb8c1SAuEFLRhTGjvBkWHsFr6Vm-NSQqKZPA3APWpjS55-wUV4tnmc0PXyuJ-cqLT07WqaDFruNw4ijX3U2hnUNRPzDwQXaiSbVBaaADWbqvVy1wEhBP0yj0QveniZnfXzjPmOqpGhSw-3DKDwIkl8uJhFu8nBb5bq5Rlg", "name": "Masters Fine Art Conservation", "rating": 5, "id": "a462c2eef4e22ea319485ae7b84f3d20756cbdd1", "job_title": "P%26M-Onshore", "place_id": "ChIJp8u2bZvAQIYRbosnWz6cVmY", "address": "1612 W Alabama St, Houston, TX 77006, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.3876169, 29.794149], "type": "Point"}, "properties": {"photos": [], "types": ["art_gallery", "point_of_interest", "establishment"], "reference": "CmRRAAAAcPUKMLmgniI5K53EsOTJxDRCCZrA9QASbATDip2r_yWvgQux-rS9kTwbwWw85YkjDI1kyH3EECQKjfWnRDSuBTzjES1lVRyRGV1_C4oEr239iFOFVB9XW1zD5-fCeTUqEhCFwyyvNq999TOvbcBnxgT-GhTHMnTvuVzNHiofBnfqfE0pBI_thw", "name": "Whitten & Proctor Fine Art Conservation", "rating": "NA", "id": "883a8c5ef35ab28e1630235ad65a6b16506a67fa", "job_title": "P%26M-Onshore", "place_id": "ChIJ8YuXE6K4QIYRn1SF1hazFEw", "address": "1236 Studewood St, Houston, TX 77008, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.3858767, 29.7300997], "type": "Point"}, "properties": {"photos": [], "types": ["point_of_interest", "establishment"], "reference": "CmRSAAAA1-tXd0bX-Pna1ZdXHvPDtxLHUPDcf_PIX9_-jFZ2xFjtRkIZIqm9RTaFze6T3b5FSe428ZvfWT5QEZnE5iaCN3RA87QFo-nuB1vIJQMXG0t4ISsLkKpqr-4jOCzmoPbREhAh5jVyj29ut-cGXNrMsRZlGhQyfNCkj91fNNSwtXtdBHNZY5sFqw", "name": "St Mark Fine Arts Conservation", "rating": 5, "id": "ea2d4bac6d74716b33f456dff3aae0cc0b43cca3", "job_title": "P%26M-Onshore", "place_id": "ChIJKbDEoXm_QIYRcRFBlp0dE8A", "address": "4901 Main St, Houston, TX 77002, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.483218, 29.7482286], "type": "Point"}, "properties": {"photos": [], "types": ["point_of_interest", "establishment"], "reference": "CmRRAAAAXEnHjrSFIE-5h8ZRVudZEn-7Kl2aQkozYbpBv-ZT5487ge_ubY3GZX91aalnfSQaJkFxoQRxiXTyk5bBCRIXfxcwLBaHbA4ZAW7ooCSAAHcqwQVHWpW7YLww68jTZ0CgEhBzyo2C-83bIlM-SM5aiVnDGhRm6C_hUz5ph23O4wUyqQdHPIvjsg", "name": "The Nature Conservancy", "rating": "NA", "id": "90af6fb9fb926dde9f7103577cebc4150bbb1dec", "job_title": "P%26M-Onshore", "place_id": "ChIJq-m4EX3AQIYRJkn4Lhccp2E", "address": "1800 Augusta Dr #240, Houston, TX 77057, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.42318089999999, 29.7345943], "type": "Point"}, "properties": {"photos": [{"width": 750, "height": 437, "html_attributions": ["<a href=\"https://maps.google.com/maps/contrib/106788706324997826205/photos\">Erika</a>"], "photo_reference": "CoQBdwAAAK8tgr7S2ZisIzcF1cPDE79QZvg6oQhhUjVOXfdSH7l3QBg40phvWOm5BRBXlmTlRvp5ckrxIjDG2LKdlxVW_aRac4NARbsZAt2XiSPOqDqnnDBdnaLqJZ0-UxbhzwNVVkO8xka2Gwi2usdZwr9c_oSeR-KmInmFvqicf8siFOQgEhCf3hWgWef13AA3k7bicj5-GhRmRfXyDxbHpBpDsfL0KwLVAP0zkA"}], "types": ["point_of_interest", "establishment"], "reference": "CmRRAAAAteGiWmDtp9s9vD3KdW7hX_eyGQzzPu3Q1xd423HSVcMSkLsph8URio18pen6jy4xN0qZJfsaQJ6Ia4kWZXXa0WJNz0qPrsM_5CFp_OPkOFK2fSVsrxVX_b9f-l60VwOiEhDTKOl6Wmy_rLJNONhYFgxNGhQeO9Weem95g6Q6GGPcqiec2KAwbQ", "name": "Student Conservation Association", "rating": "NA", "id": "1c5ea7722fc0d99e9f7dfca55f5d9078224d51d3", "job_title": "P%26M-Onshore", "place_id": "ChIJQcqBXfDAQIYRErawO-goGj4", "address": "2990 Richmond Ave Suite #400, Houston, TX 77098, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-96.038102, 30.055621], "type": "Point"}, "properties": {"photos": [{"width": 984, "height": 985, "html_attributions": ["<a href=\"https://maps.google.com/maps/contrib/110279808588468038448/photos\">Peckerwood Garden Conservation Foundation</a>"], "photo_reference": "CoQBdwAAAFuu_bbKOTFHEFDH6aLWuP8bt4TbM6-moMxPXLWmShv2vtJwgLFYCOw8xTL-Xu4Nkcpq_zdrWYR2pzGyovQkizMQunuGZHoHpPaL0iRkihrf-h8Nn56xxoA5e9qhDHzDKkRWIvJII3qaURVh-ZT0AY2zVndvmI9VWNYO0HMLobpdEhCCMAiElqAFAO5RHdvpQCD3GhT8zBHFdOz7cSbVYz9vEPxfHtT_LQ"}], "types": ["park", "point_of_interest", "establishment"], "reference": "CmRRAAAA3WGCMguX32neqyQOg34SnS7g_9hkjv2o5DTeBvIM9cG_MsolyvhS0zmoGzvqgN8OjYnfd277ue_0MZ-zGFnhZ2BwLuQ0ykDMZh1N1XZsrqYF1Kwo90k44Oc6-cRraKgHEhBb0uQXyYafc_u06NwluD0kGhTtoiXzYx2e7WAo98CleUk_YgGg9w", "name": "Peckerwood Garden Conservation Foundation", "rating": "NA", "id": "e618a4c618cd67ce4f5fdc165f640220ab3b53b2", "job_title": "P%26M-Onshore", "place_id": "ChIJmUR7pvHKRoYRIIl0o73bPGE", "address": "20559 Fm 359 Rd, Pine Island, TX 77445, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.64386449999999, 29.7515036], "type": "Point"}, "properties": {"photos": [], "types": ["point_of_interest", "establishment"], "reference": "CmRRAAAA_FjYCzBlbywdIYAjnnqR3tQ42vDheSwQeGdPHbVY37NsHjG5oa3HOBf_8cqJFeXyhQKu05t74yzza-y9QTP0FZSSYrABZxggD9k-Y5wNzbqBEKh_1IKlqiGT5K-q9fyWEhB50EJy1gB9SRf_1cyoUxU_GhTInCobvGMaq3XXO7wOhyseMqW5EA", "name": "H2O Conservation Technology", "rating": "NA", "id": "30c07988ef8dfc62dac712b9d587daa4a36f2539", "job_title": "P%26M-Onshore", "place_id": "ChIJIWZRKeHKQIYRXxta3wOMGGc", "address": "1725 Hwy 6, Houston, TX 77077, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.5705632, 29.7714443], "type": "Point"}, "properties": {"photos": [{"width": 3024, "height": 4032, "html_attributions": ["<a href=\"https://maps.google.com/maps/contrib/108143329814504597326/photos\">State from Jake farm</a>"], "photo_reference": "CoQBdwAAAC7d2koY1cjnS4ytIAHs9ujVhmdbKO9FZRAHImPBdFOtda41_IjDToN_R5oFLRUlXAgZUg67krOKLRONhXDuW4Kq8ChxBwsoRYnLJ5rKSgdRy5DgEwAeKbzWOenH6TzzuQXQqPF-5cUqHh42a1R0XU2mXOdrwXmdJESoeE1P2zxTEhDkmEhP1tHFA0RgycOwQ80mGhTTMBZVaKcHK_G7xMFY6AZqeW0T4w"}], "types": ["park", "point_of_interest", "establishment"], "reference": "CmRSAAAAdRXH8jsdA_0dTe143zJtB0QKy4CiRxHWUtYo0MojDOFzntnc6zrRnFX-BniGgYOzoUu0Y_rjzX6vouYk7As9KEHAXdvYCMLTgeYsE61YMwfrNT_WuTi9KzPT6fbXM85FEhDbmgUxgaQPESpnytZtorpqGhR9fy4LzZkU7k6YHu51T4HUln-B0g", "name": "Houston Audubon Society", "rating": 5, "id": "050a5458d86bdd1cee7b09678bd6256d0a20a73e", "job_title": "P%26M-Onshore", "place_id": "ChIJlQOxwVDbQIYR2uX_TZl0TYc", "address": "440 Wilchester Blvd, Houston, TX 77079, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.56820189999999, 29.770778], "type": "Point"}, "properties": {"photos": [{"width": 1800, "height": 1200, "html_attributions": ["<a href=\"https://maps.google.com/maps/contrib/108765250995932379967/photos\">Audubon Docent Guild</a>"], "photo_reference": "CoQBdwAAAGJB3ji80aY9kqcARO0Oe-kI74sbe7LnS5MTwxHiumOygd2rVfi_M-IksX0pbSEBugMnw2GJKZG-54ewKi5i0L_sk3IgU49Q5LP9MHOXLPN_3VVopnxnE7NvJw77FG8V3QW3QR1axKxEw2v5G1LtVfTsmLzpnFKfU1o5WN7IUArwEhBQ9qo2dFzLFoK-LCQL8y1jGhTTLff-uXtfKq5GhzoDs5quR0Rv6w"}], "types": ["park", "point_of_interest", "establishment"], "reference": "CmRSAAAAPsmAG9Eb6fZbMMUi2reMsVmPFQ27hHRnsIcJ4ujAuwH5kgMh8ItbRLM8vzJFdlcXq3S8DtC0yL77LRzVYjHUqLn5ZpPomPReWldItyPPGg1NohHL6OeElWihQZ-6WRO0EhB16rNr2i8HEvaxoW2LNyOfGhSwAx7YZro_dsLsNr9Zz2VolwxYJQ", "name": "Audubon Docent Guild", "rating": 5, "id": "7ddd5daf76cc4979e2ba6b062322d1c77d5d1c07", "job_title": "P%26M-Onshore", "place_id": "ChIJI9XyNFHbQIYRtwHb8EtTpeU", "address": "440 Wilchester Blvd, Houston, TX 77079, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.44932349999999, 29.7803218], "type": "Point"}, "properties": {"photos": [], "types": ["point_of_interest", "establishment"], "reference": "CmRSAAAAvgCf_qBN2PU728pYAvcIFDbg2qCplE-nzcqvLYKaGa0hpMEfoZVi0bdnphm2_ueHFxnmeWt9VUz0sPSwWKoi0x2aPaY5oNGhtwjVpEBrZFpkpudygcmtFmiPdMLhK95tEhDb-SANhxMSB7OiW_ZamKgzGhSzRahKd9v-pM1MfpyQ_UbovqZDlA", "name": "Coastal Conservation Association-Tx", "rating": 3, "id": "7258b034e119f31e82320bca6e72781ee9f79d75", "job_title": "Tetra-Tech", "place_id": "ChIJcekacM_GQIYRPzL13cgQrPk", "address": "6919 Portwest Dr #100, Houston, TX 77024, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.47039, 29.655454], "type": "Point"}, "properties": {"photos": [{"width": 5312, "height": 2988, "html_attributions": ["<a href=\"https://maps.google.com/maps/contrib/101184977609161362375/photos\">aug4</a>"], "photo_reference": "CoQBdwAAAGnIU7DbqvyTQ2NZkJXcZOGQhoC2vv2SHQ5E6C1unaDEkow9lPgjn2VSSjRIs4p59cxcMbMlodzv9FIbI0owtgiAGPHED0-DBmLiBFvQQ1orZe_qlaA_NJqA6DZhDY3bGBHuYusVBOXAx8aaMKAskf-MFt9kcwFQu2GfvemyRUwyEhAdYRyiD9jnHo5gPCg8Q20lGhR6bVBbuFbI4RBJzrhU-GPARRpt0A"}], "types": ["park", "point_of_interest", "establishment"], "reference": "CmRRAAAA7yoqvHF5Ht16AVQFWQHElmOdC9tOSEydiZHHAkZ-bB6nNEZH1OYSV99COGVOeZNVxzCt08jwK3w25qMEKruXpaQ2u4dLYRuvmY_h908Cum9rIxc5eBWvzasXvFRYsSWcEhDPzZ7yUwsYudsi1anV0Ia4GhThTkDzhLnd0pGsGoO--AOE9A9gqg", "name": "Willow Waterhole Greenspace", "rating": 4.3, "id": "0127506e8071350c2d48f0ca56e939045297a0f4", "job_title": "Tetra-Tech", "place_id": "ChIJR6_2zTzqQIYRsA7wExgfDWs", "address": "S Willow Dr, Houston, TX 77035, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.4003322, 29.7388505], "type": "Point"}, "properties": {"photos": [{"width": 1136, "height": 640, "html_attributions": ["<a href=\"https://maps.google.com/maps/contrib/117056878997299689379/photos\">Marisol Brown</a>"], "photo_reference": "CoQBdwAAAAQZoM5s7U5W2iR5gJJOa_nN63V95OqGYN_aP1b-1_sVwguFlfVdXFLk8eAGZudP02kVAO8yYtrOvCFkZhnNLS1CSygDN1pCYbHCo4K4Z2svhVH9N8qpQ5DVb07TIL9RvH7UKFebZR2OWnY-ryZ2wR8bJVrFcIBuT0RW3nfzewCTEhAdNym-NOzkdl9dQxT1eVWUGhQpPCYvXugs_dODApQN9oyFWQ4OZw"}], "types": ["point_of_interest", "establishment"], "reference": "CmRRAAAAIyMtW-M7iQEXYc9kOSdfE_VCvAbJUfxrKIzjUEbQDCV6mf3T7e1PTyNy9l2CEHDAD_rJL-1z0eI7J-WxMgJ8zzCTXq844csqe4O12ChN2a7QFmlaPbwghG7Pcdz9ZkjVEhA5vYGjKwwz5sgsIFipmwNaGhQvDSCDXow9DuXCp-1welycQUHKJQ", "name": "Masters Fine Art Conservation", "rating": 5, "id": "a462c2eef4e22ea319485ae7b84f3d20756cbdd1", "job_title": "Tetra-Tech", "place_id": "ChIJp8u2bZvAQIYRbosnWz6cVmY", "address": "1612 W Alabama St, Houston, TX 77006, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.3876169, 29.794149], "type": "Point"}, "properties": {"photos": [], "types": ["art_gallery", "point_of_interest", "establishment"], "reference": "CmRRAAAAooeFj-gPF-TDRlv5I0qGUVpHsd3KLPXUL9sRfNvPf7Y1INi84kiVT52CSjBfhtuvexwjr-LvZgQAcq2hKmEIxpclrlfH7LCTCl5tlqKkomO2XuiblQezsvoIODeks0XlEhCs8jBQjsx5LtUUiaaNcpBlGhRAGYF6rOy-I6V0BNNgHjdoqshtZw", "name": "Whitten & Proctor Fine Art Conservation", "rating": "NA", "id": "883a8c5ef35ab28e1630235ad65a6b16506a67fa", "job_title": "Tetra-Tech", "place_id": "ChIJ8YuXE6K4QIYRn1SF1hazFEw", "address": "1236 Studewood St, Houston, TX 77008, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.3858767, 29.7300997], "type": "Point"}, "properties": {"photos": [], "types": ["point_of_interest", "establishment"], "reference": "CmRSAAAA8kE-KikT8_9uuBJeWcYtgwzD5PT_G3YZvVmut8gvqnccZGdenuOdX6kWKqQQtVqhqhWQ6_7l3ZwoFCaGuRmfdwy9sdB2wvtaeuO-g0QNW0YduGRqiqi9MS2fNCzy210hEhDZntN5pGX4hWc2UYHqR-xoGhRUKfqIOtyjxFyt7GQRA4WJr7t3QQ", "name": "St Mark Fine Arts Conservation", "rating": 5, "id": "ea2d4bac6d74716b33f456dff3aae0cc0b43cca3", "job_title": "Tetra-Tech", "place_id": "ChIJKbDEoXm_QIYRcRFBlp0dE8A", "address": "4901 Main St, Houston, TX 77002, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.483218, 29.7482286], "type": "Point"}, "properties": {"photos": [], "types": ["point_of_interest", "establishment"], "reference": "CmRRAAAAaq3KL11Qdo0dlidziNogQ6MpigoMz8cfFb9HGYClj03Z47vfI1jr6VReEb-rnYeTr0Z66brg6mZLxpKvtfXYrr53Xt5TMP1HFFYw8wCjRCNmeKC4yVO8vGKgltv4mi0MEhAqgZ0n7Uy6ZG66helTv9YkGhT3MWZRBOUrKzn5wJHlKAz00zeVjw", "name": "The Nature Conservancy", "rating": "NA", "id": "90af6fb9fb926dde9f7103577cebc4150bbb1dec", "job_title": "Tetra-Tech", "place_id": "ChIJq-m4EX3AQIYRJkn4Lhccp2E", "address": "1800 Augusta Dr #240, Houston, TX 77057, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.42318089999999, 29.7345943], "type": "Point"}, "properties": {"photos": [{"width": 750, "height": 437, "html_attributions": ["<a href=\"https://maps.google.com/maps/contrib/106788706324997826205/photos\">Erika</a>"], "photo_reference": "CoQBdwAAAISit9iqZX9whcYxKF7iTCpnxSgHYXMWjQX5Ch3tmTas26dBQx28OfKmRzxgmBTTuJLGpUp2FkgdlRh01b64xE4-LvaSxnM4wMM_gQAtb9Qe9kdfYD7qKQ3STGFuMG35Ex7OB3L4bWsQmYblsd7fQMSQaayel3niMy_uDCGKcQ1wEhAs7Cna7amRW6KuljRgkmoAGhTCM1ukci4EavJBridJIycGoglGqg"}], "types": ["point_of_interest", "establishment"], "reference": "CmRRAAAA4nl92ceHgD5YxOf4hcvGmSWU8LHqGNQxm41aY2A25oBLwX63bWtRgozMHcwymcC2A10oUTDctfA_SKBCkIJPAiHV6_utPOfoRH4rvZwLIOIx3kOHO5Vneop2bDpDJa9AEhBV-nogga-vllfm-GbuAmWYGhQy135Q-CMODZGRN0DHVxvk0qM9Zg", "name": "Student Conservation Association", "rating": "NA", "id": "1c5ea7722fc0d99e9f7dfca55f5d9078224d51d3", "job_title": "Tetra-Tech", "place_id": "ChIJQcqBXfDAQIYRErawO-goGj4", "address": "2990 Richmond Ave Suite #400, Houston, TX 77098, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-96.038102, 30.055621], "type": "Point"}, "properties": {"photos": [{"width": 984, "height": 985, "html_attributions": ["<a href=\"https://maps.google.com/maps/contrib/110279808588468038448/photos\">Peckerwood Garden Conservation Foundation</a>"], "photo_reference": "CoQBdwAAAM4TrE4Jvsk9FXBmofwVvTtTZCqU8ae9F0bb3_Q9YqCOnxL-a4HSKuQHAJPNQ2KgPYh_yRHLZ4rJsbzd2Z0ogrOuDzLV6zHkTK_Zeu9MWBjkMCR19Jo-0DNYF9zLvguINsxbUaagr5c-WubpTxftC71-T-X5Eb_F33Wae8KzOlVYEhBl6vIhK0YdmKnq3a5sttSbGhTW8vf8ci6b25etIEHi9bY74XE9yw"}], "types": ["park", "point_of_interest", "establishment"], "reference": "CmRRAAAA-upk2HI3hxyNEPkxq_kFWbnqXkXhfQf-MDFt7gdlQv2XM-kgAZaGz0RykQl5Wd2z7jO-hMQM2CHugX1EuzMoVAOdAMCoG2wCmfc28Mzf1Lpp4UxgcTvsGjIP4MkwhmPeEhDefksxps36UTE4yoDa9ARcGhSKRTR5fqLw-TRJzaAUNbdXe35WGg", "name": "Peckerwood Garden Conservation Foundation", "rating": "NA", "id": "e618a4c618cd67ce4f5fdc165f640220ab3b53b2", "job_title": "Tetra-Tech", "place_id": "ChIJmUR7pvHKRoYRIIl0o73bPGE", "address": "20559 Fm 359 Rd, Pine Island, TX 77445, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.64386449999999, 29.7515036], "type": "Point"}, "properties": {"photos": [], "types": ["point_of_interest", "establishment"], "reference": "CmRRAAAAu2LPFrDKJb6XwdwC8WC9TMaOPCpE3qKisJMc6kYZBwj_jPs0MkCIR-4gnTMmQp_cVWI5snFbuBUgD7eEzcNhaZ-0O9qzdscOxujR2LWkzrDQsOBJGXNeXr4ziZqg6pGjEhBUDGYPiSYQYDR3U5g-9u_JGhRXyztkgi2JV9VwPb0Nn5_3yk8otw", "name": "H2O Conservation Technology", "rating": "NA", "id": "30c07988ef8dfc62dac712b9d587daa4a36f2539", "job_title": "Tetra-Tech", "place_id": "ChIJIWZRKeHKQIYRXxta3wOMGGc", "address": "1725 Hwy 6, Houston, TX 77077, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.5705632, 29.7714443], "type": "Point"}, "properties": {"photos": [{"width": 3024, "height": 4032, "html_attributions": ["<a href=\"https://maps.google.com/maps/contrib/108143329814504597326/photos\">State from Jake farm</a>"], "photo_reference": "CoQBdwAAAIy6gLq6xUWa7QrMwqSZ93twMlkMPMHuXiY0fW8h-BKKNvxQnGQmfUPcTfvjwdUXjusVFAyAQDviwZyxogLu4YYoCAEIWudP1BVVLVThikdr45yeircKhKRFXk8BkYd0itmdo365M4lqdkBhyKwPNYybuIEHHvJ_gUUeByoat_9ZEhDJMYlG-J9RUeL4fzzrWWsGGhS2sqcfmPek37fZatCKlYIl6j-xoA"}], "types": ["park", "point_of_interest", "establishment"], "reference": "CmRSAAAATkf4FdrB3n9yOi_els2UVBRsbqPNh9DE72UKd5W9KsA6VipODQU-yx1SiwwJLETS-lETD7lvT0-CXfGYQMH2E4JJ0wYT3Y48iXlc6khm0reHWPlWyprDpZkqY3hAHspFEhCl9lV9-iNJXSr5j5VGVuEjGhRWha06EUOiitcvaq9RKTfX1i9Onw", "name": "Houston Audubon Society", "rating": 5, "id": "050a5458d86bdd1cee7b09678bd6256d0a20a73e", "job_title": "Tetra-Tech", "place_id": "ChIJlQOxwVDbQIYR2uX_TZl0TYc", "address": "440 Wilchester Blvd, Houston, TX 77079, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.56820189999999, 29.770778], "type": "Point"}, "properties": {"photos": [{"width": 1800, "height": 1200, "html_attributions": ["<a href=\"https://maps.google.com/maps/contrib/108765250995932379967/photos\">Audubon Docent Guild</a>"], "photo_reference": "CoQBdwAAACqtcdXpOfseJnYhqiCOKedsjtPhWXmxlVONSAWpQqz1w235KlV0ku_uJbqLm2pX6PQKEPaEAv2IyUN3o9A1x971f_iD9b6Vr_mRUlgGItohur6_QRSZq8RoQzhsHAkCLMTxQUrmYXa5oBBZbmuCKjA-DS6NtLrdMDVeaGUaoYJqEhAVli3z9HYH0h7S_UizTQRTGhQ_iP0BS9DjfwgA3I1qNMRu-9bEdQ"}], "types": ["park", "point_of_interest", "establishment"], "reference": "CmRSAAAAKfujWSlfpZApPXMpLmeFvpneCJRnKdcxV3uIYT8iOkeZo5XOOhrxAfIJWsGVEKeCp1Q4fL60Cj8Pt6YubcOmAPRkVMPY2sZnAlNv1DiKJl3ZwTU2zKKcePSfOXqDVHoyEhBwOBVPR7vB_g_lGuDNaTicGhQ-SsunGbpDOXWssAzg8CrXJEa05Q", "name": "Audubon Docent Guild", "rating": 5, "id": "7ddd5daf76cc4979e2ba6b062322d1c77d5d1c07", "job_title": "Tetra-Tech", "place_id": "ChIJI9XyNFHbQIYRtwHb8EtTpeU", "address": "440 Wilchester Blvd, Houston, TX 77079, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.44932349999999, 29.7803218], "type": "Point"}, "properties": {"photos": [], "types": ["point_of_interest", "establishment"], "reference": "CmRSAAAACwB7LsnyADUvHD9yhfBWfYMGEhaNNRm5A6Ggvx-XT2eIZ4uvfnGiS73YyzsPJdPtTrf-iRripE9d9_wKPYb0pZ3yfqtjxORD3V3l82Ip3Du-YplEFGhiv1s1tV7BRBWIEhBlmUF78ajvTF6BTomFNnU5GhTJr8n0enC-sY4dI6V4evHWF83jqA", "name": "Coastal Conservation Association-Tx", "rating": 3, "id": "7258b034e119f31e82320bca6e72781ee9f79d75", "job_title": "Set-Environmental", "place_id": "ChIJcekacM_GQIYRPzL13cgQrPk", "address": "6919 Portwest Dr #100, Houston, TX 77024, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.47039, 29.655454], "type": "Point"}, "properties": {"photos": [{"width": 5312, "height": 2988, "html_attributions": ["<a href=\"https://maps.google.com/maps/contrib/101184977609161362375/photos\">aug4</a>"], "photo_reference": "CoQBdwAAANgFyDAYuGvfJo1lXLHvgR7KsJWH5A1zBYrtxsFurO0dFHtIeSo40yT6RCPHkxIG15zte-51DXG5HcbaBwDpunPo099B6xZWg73u75IvI01rNTZXP3p9W7726QtaB4UR3gasU286_0zo6FmG00WMkAqPVVadw8ynNAXNoA3fy3V_EhDLxQIHISZkR8OfC6PQUoFQGhTww-a4fznehYQs2YNGTrwtgZqtOA"}], "types": ["park", "point_of_interest", "establishment"], "reference": "CmRRAAAANOR2TFI6eYaO4l4fbtk3lItH5Geo4J0fp3-piobURcYie6PDF250sM-tLpV6aR4h1N8GygN2O5-AoimyfqcZ68AbWoFOPLqRZciWT4k5aKyuWNYe0sozWZ3g1AC6A1TxEhDP13lfUx6z20jF8EAfOa3YGhTEEP-1zpzECGqX0euOle6RJdsHHg", "name": "Willow Waterhole Greenspace", "rating": 4.3, "id": "0127506e8071350c2d48f0ca56e939045297a0f4", "job_title": "Set-Environmental", "place_id": "ChIJR6_2zTzqQIYRsA7wExgfDWs", "address": "S Willow Dr, Houston, TX 77035, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.4003322, 29.7388505], "type": "Point"}, "properties": {"photos": [{"width": 1136, "height": 640, "html_attributions": ["<a href=\"https://maps.google.com/maps/contrib/117056878997299689379/photos\">Marisol Brown</a>"], "photo_reference": "CoQBdwAAAJgGxYuJ0t1BXHObaY3FW4WWsdVJDeuyw03PA1wQAaj6eM2tvLI346od6rHclaUOc0JDBFZ6zgMNzqFXWh1XZjP6ygFzrMsLyDVvx8QTJh6tTjmeMx2fiJYQNHlMTMkjQwRmjwMA_TC_pHjSft_0Rqkwwlk4-hu7fNcX6ymVQ41rEhAKw6gWoXKNbpQedHEdGCwnGhSBfWsl6_rRS4_de-RYJFhNjqIcuA"}], "types": ["point_of_interest", "establishment"], "reference": "CmRRAAAAsqUWCzKuFoJJ8tQiRUORwKCLtnL6x_p-SEwi029alpGMyYLCboLIRc61mI0x_wEOfLdkcgHxM6xCrrosTBa0cAAxc0DIWLmiUbj7_4TeFTod-vKAmoeP8QWTUjyDRpsDEhDsA5YCtA7t33Z-aYOLxrD_GhTmVgf3wbz0IOzpuHfK6lMBVgA0gg", "name": "Masters Fine Art Conservation", "rating": 5, "id": "a462c2eef4e22ea319485ae7b84f3d20756cbdd1", "job_title": "Set-Environmental", "place_id": "ChIJp8u2bZvAQIYRbosnWz6cVmY", "address": "1612 W Alabama St, Houston, TX 77006, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.3876169, 29.794149], "type": "Point"}, "properties": {"photos": [], "types": ["art_gallery", "point_of_interest", "establishment"], "reference": "CmRRAAAAmxLQkgvoZrLpCy7M6a_TZdza-4KApc71AZiaDi3C5X54FXdM6wX9vqOasKTfJIpI0IFQ-iHsthpfijXrErxIy5oS1EbPKyiDzaBbi29Y-G5eB5uX5H-5b4ioMhq_TndwEhDIxTSYHzY0sOSukHpAo4kcGhTNBAAS2tL7pPKIUE6Xg7mPvo1z4w", "name": "Whitten & Proctor Fine Art Conservation", "rating": "NA", "id": "883a8c5ef35ab28e1630235ad65a6b16506a67fa", "job_title": "Set-Environmental", "place_id": "ChIJ8YuXE6K4QIYRn1SF1hazFEw", "address": "1236 Studewood St, Houston, TX 77008, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.3858767, 29.7300997], "type": "Point"}, "properties": {"photos": [], "types": ["point_of_interest", "establishment"], "reference": "CmRSAAAAOglRCVyhfqUkERbXQCbxGT2GORI__T4Dizkighou7z2Y5ZMufLdI91UZ1qmBB2eplWgQhT5PGQScg8FaT-iHmJHp2k7JfNgJSZS-aOLkf8Jyb9oXfjEuGFET1ntS7PqZEhCy5C4sgS4AwJXCTOqznrf_GhTv6ei9z8JVLX_VnC1DlTp2BZTVqw", "name": "St Mark Fine Arts Conservation", "rating": 5, "id": "ea2d4bac6d74716b33f456dff3aae0cc0b43cca3", "job_title": "Set-Environmental", "place_id": "ChIJKbDEoXm_QIYRcRFBlp0dE8A", "address": "4901 Main St, Houston, TX 77002, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.483218, 29.7482286], "type": "Point"}, "properties": {"photos": [], "types": ["point_of_interest", "establishment"], "reference": "CmRRAAAA4C1-bkUSf4mTYkYHAjeMYZZ-EgPDST1Vl1O0QJR3ukctZXxs6oCdirZCtU3nLfRaAX3Gyx6qWY-cKhfvTN_rW_lKdgUlM7OVshZmv0I2CcPv-ALX8j4pw9v20tKXiwoyEhBsAMlPCKRbtVQNWm9NxiFXGhTxKUjfb2aAxfPcTapxJkw4KU3mgQ", "name": "The Nature Conservancy", "rating": "NA", "id": "90af6fb9fb926dde9f7103577cebc4150bbb1dec", "job_title": "Set-Environmental", "place_id": "ChIJq-m4EX3AQIYRJkn4Lhccp2E", "address": "1800 Augusta Dr #240, Houston, TX 77057, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.42318089999999, 29.7345943], "type": "Point"}, "properties": {"photos": [{"width": 750, "height": 437, "html_attributions": ["<a href=\"https://maps.google.com/maps/contrib/106788706324997826205/photos\">Erika</a>"], "photo_reference": "CoQBdwAAAEu2PD5mvYyPRzXh-psbwEUPgz1v71ezEVCsE7agaXwsJBZmOwAjBwBnUg7eIZ1NQCuoUUa7y-_HfCyQSSB_6c_9WcX-ojvGMH_k6v1A9yUdHdVjdqt1rv2RA9Em0mAy1qy93l_db9dBEiV1qGW_GKc8F4WcBMHkGBXxRiy-JPKvEhBngOAB5_4O6FzVt66v6G5AGhRBpZmlCOeygw8MCP5EJfxKa0qSaA"}], "types": ["point_of_interest", "establishment"], "reference": "CmRRAAAAKsEdWleZHffaGdI_OWlMamg8d3WWUCRtusmOk2eZWcwX3aQI5Pd1iJFCy17ISYPf_qJMUOljUupGpt9A_QYnTr3A2snC1XINpr4HL_zD3RLNuqQJwgnMLrNQtTbVvkW5EhBSkgI50lSQ1z3broZ4Y-exGhTm_OWQPhXkBRTcMS250me3RLH_HQ", "name": "Student Conservation Association", "rating": "NA", "id": "1c5ea7722fc0d99e9f7dfca55f5d9078224d51d3", "job_title": "Set-Environmental", "place_id": "ChIJQcqBXfDAQIYRErawO-goGj4", "address": "2990 Richmond Ave Suite #400, Houston, TX 77098, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-96.038102, 30.055621], "type": "Point"}, "properties": {"photos": [{"width": 984, "height": 985, "html_attributions": ["<a href=\"https://maps.google.com/maps/contrib/110279808588468038448/photos\">Peckerwood Garden Conservation Foundation</a>"], "photo_reference": "CoQBdwAAAGTdTnrv_XQpF-RXMiExzIqlRLSOB4B4Fr9Xo9ths8BAl2LUhbUxDMGVUDT2-m90_JQGWp7f0SracUah6t1Kt56WqrCoLBipmBwRCH6s4uL_08mwMWHU9ZVHbuPsAuEJZcpCSHj4muiTEZ1LZmG2AVvmCiCwTjgViag0iw8jo8H3EhD9QjdOw13Rl4uWoZwBmyJtGhRAHbFWaMX8nt4WK4lbmt_rt4Xztg"}], "types": ["park", "point_of_interest", "establishment"], "reference": "CmRRAAAAk8FlyMloVUpSpAVmBiWr54iGxNKPpsppR6GgCh4GDaW6iWTqG3_Z1hMsg0PYFk6hEUjkZt4TZUYK9EVcYP4OZvYS68QbU8gGwcoQvu57W3whia3B88Ff0_mL1Y4kk4vUEhBtn-Rd1f6KdE7Cjdy_asf-GhR63nOJHkmjjMNQtRp9iTogzA1vLQ", "name": "Peckerwood Garden Conservation Foundation", "rating": "NA", "id": "e618a4c618cd67ce4f5fdc165f640220ab3b53b2", "job_title": "Set-Environmental", "place_id": "ChIJmUR7pvHKRoYRIIl0o73bPGE", "address": "20559 Fm 359 Rd, Pine Island, TX 77445, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.64386449999999, 29.7515036], "type": "Point"}, "properties": {"photos": [], "types": ["point_of_interest", "establishment"], "reference": "CmRRAAAAHBiFIe0ilNczHu69aVbqFXkab7Kpjg23RJvGgq6w6_IEaVIuCpCHkiQzOi07rs4weg0gwcZpmAzp8uGvahj6i0oo6TZoE81eclA1TUdOdZuvj58XQithnj67e7EnV_YKEhA8cfSj6oSVoazuWQAQDw_PGhS9zKjAjfbd-UOS_54GnyELvyuTOw", "name": "H2O Conservation Technology", "rating": "NA", "id": "30c07988ef8dfc62dac712b9d587daa4a36f2539", "job_title": "Set-Environmental", "place_id": "ChIJIWZRKeHKQIYRXxta3wOMGGc", "address": "1725 Hwy 6, Houston, TX 77077, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.5705632, 29.7714443], "type": "Point"}, "properties": {"photos": [{"width": 3024, "height": 4032, "html_attributions": ["<a href=\"https://maps.google.com/maps/contrib/108143329814504597326/photos\">State from Jake farm</a>"], "photo_reference": "CoQBdwAAABAhL5sJmmdZPEdcWRtLknQqJnnt8i0JFuzMi7aDP7ub8fslpGZXgX-xIX1Oq8veIVABctzVn1_3WRaVjUizqlVEYj1zom5kEzR1c10zxfA44LjH0LnGxb0K2tWjCYCsiCIYg4IxlLs5RzDBS5II714SSoRqibOBv1qHMKKMi7S_EhBc8obWPuZ7zYrxhp3ZktJ4GhTRyrFSc5zusjzImpY9rNukDogJEg"}], "types": ["park", "point_of_interest", "establishment"], "reference": "CmRSAAAAEqZ9IEJ7Ruc0zyZmc96mSMLIyuqMYkUyc3uRVFPLzQWLAg4tdl-Hn_jNCiEVoayoRi6NF7ZgsVoK91zc_2ROQkeTbyHYUD_y6dZjoF2vdseOuC422WeMLVp7Vr6zm9BEEhA2o8Q-Pjsfl96SdTkz85xWGhSXjAMj35iY7v8L9zUkNUc7sHAOlg", "name": "Houston Audubon Society", "rating": 5, "id": "050a5458d86bdd1cee7b09678bd6256d0a20a73e", "job_title": "Set-Environmental", "place_id": "ChIJlQOxwVDbQIYR2uX_TZl0TYc", "address": "440 Wilchester Blvd, Houston, TX 77079, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.56820189999999, 29.770778], "type": "Point"}, "properties": {"photos": [{"width": 1800, "height": 1200, "html_attributions": ["<a href=\"https://maps.google.com/maps/contrib/108765250995932379967/photos\">Audubon Docent Guild</a>"], "photo_reference": "CoQBdwAAAJdjSChumsqiV0J_ThPnJRo7u_dgxemD9RgeD5j8zy_6fWWrnxWh0NJBOEvOby5WcCrMRCFUtHLGVNayFCLCZUo5tGJ2uHC_8b7WnbF_BGQJvJD1zwaLPNU64OO53l5R4nb-Zbd7iugd1UPBtuEs96Pcuqm9a0zDIi3nvX8MmDCMEhC-UJ216kO3YJNy33Gakh6PGhQ2u0gfdnu-ob8c2oXOCOH9W9vp9Q"}], "types": ["park", "point_of_interest", "establishment"], "reference": "CmRSAAAAbE8Avp57WrVcEDPqI2GnrOMicKcFDJg_s2lE-JpprQ6_qkJ3ddH0XrWCd3ZWFPEIy3akVsPERot6w92fCT-C86fNw9PkK6143pDwVFHD-N5BukgE7DmpqWRyDwX8OknNEhCPMpyYyjwS5WI9F0JeqstwGhS0iu2g9qJhPZtIxYgo3Nz6BK5dfg", "name": "Audubon Docent Guild", "rating": 5, "id": "7ddd5daf76cc4979e2ba6b062322d1c77d5d1c07", "job_title": "Set-Environmental", "place_id": "ChIJI9XyNFHbQIYRtwHb8EtTpeU", "address": "440 Wilchester Blvd, Houston, TX 77079, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.44932349999999, 29.7803218], "type": "Point"}, "properties": {"photos": [], "types": ["point_of_interest", "establishment"], "reference": "CmRSAAAA4Q776R_6rwwic-xAVOcHnmlTvPT1jH-g2OHKRA6qWSFC3Ekg-0kDxlHLS7WPFpkKSzFSynOMk-od9afVhxaJCdz2mEQXXMu17Ny2KmlMf1QTNKr1379XgR-iVOdt9-FwEhAWEjeiP6mKCHxa32ncD0pWGhSZbuje2csESqor6YUGiNK8ETvQow", "name": "Coastal Conservation Association-Tx", "rating": 3, "id": "7258b034e119f31e82320bca6e72781ee9f79d75", "job_title": "Lpc-Personnel,-Inc.", "place_id": "ChIJcekacM_GQIYRPzL13cgQrPk", "address": "6919 Portwest Dr #100, Houston, TX 77024, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.47039, 29.655454], "type": "Point"}, "properties": {"photos": [{"width": 5312, "height": 2988, "html_attributions": ["<a href=\"https://maps.google.com/maps/contrib/101184977609161362375/photos\">aug4</a>"], "photo_reference": "CoQBdwAAACnY0IZnjelQc8sonvImpkei8jCu4Zpq4u-YnHfyvmNYreB0EBlASHPZWWLeo19meP6yuxztmU7_IeblsuU_NJSYzryNrx9deI4RJC9RL2cEz1CO0bdJsHMMYq0U-esv7UUGYs1k9RCV7grV6yOOLCwiUXLonKQYIw64W0Z8AB9DEhDxcDHGmUyfXLiC0pym3I3LGhT-rNFb8kjs5vzdcl83ujJidip8bQ"}], "types": ["park", "point_of_interest", "establishment"], "reference": "CmRRAAAA1CWi5uhgwn21AS4CXcr3dykm3zEabyKK2DE9bMSSXaE0GKIJKaRMG7cb55BA-Xs5V7soiSjNB36Im2-cxqlPbAODwyNMbsniU0ozJOXIlbdNVYsqNbJWivVN9GEFa1HwEhCwyOxw4QWFl4bzp9i_ooYDGhSdylwuluHmKA5eG-RGVxMJunTaFA", "name": "Willow Waterhole Greenspace", "rating": 4.3, "id": "0127506e8071350c2d48f0ca56e939045297a0f4", "job_title": "Lpc-Personnel,-Inc.", "place_id": "ChIJR6_2zTzqQIYRsA7wExgfDWs", "address": "S Willow Dr, Houston, TX 77035, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.4003322, 29.7388505], "type": "Point"}, "properties": {"photos": [{"width": 1136, "height": 640, "html_attributions": ["<a href=\"https://maps.google.com/maps/contrib/117056878997299689379/photos\">Marisol Brown</a>"], "photo_reference": "CoQBdwAAAM2daILGjcmPneTrYWDY5VjnD9zhV9ggixE-XxVP_-uHhFqt9SpN_MqOkip9_TqiNjvW9_1IaaX7Lgd9O7u3CZt670UK-4s1sguhIDi5c398toSqwNeKH4D4ea7G4n8hzWPLMvB4iSjRcrePafOZZDClZlrx3eKdzpWVly9xG1ejEhCYwEPFs_Ir6DDdgW5BmZNWGhRBh2ZYzVtXgG7GOYp7UD9GQXng-Q"}], "types": ["point_of_interest", "establishment"], "reference": "CmRRAAAAA5tIGfqU7mWTWyo-oJjWt5kcjWSt8ceKYEZCmkoV88JDuZ7qhkTi5wzHlZioif0uCt9aIVPJJDOpNBmsBmkG97Pw-8nkDcXCo1y_ozHjGt_DYVqlKBimI3dNh4uG9fMKEhDN683IApNYBU5eKqfk1M4MGhRbURG7yTmKL_m23U8JOxmVVY1_8g", "name": "Masters Fine Art Conservation", "rating": 5, "id": "a462c2eef4e22ea319485ae7b84f3d20756cbdd1", "job_title": "Lpc-Personnel,-Inc.", "place_id": "ChIJp8u2bZvAQIYRbosnWz6cVmY", "address": "1612 W Alabama St, Houston, TX 77006, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.3876169, 29.794149], "type": "Point"}, "properties": {"photos": [], "types": ["art_gallery", "point_of_interest", "establishment"], "reference": "CmRRAAAAzKN0t8-eE-Xuyp689sAifntGkHQREZeYgzAmghghPXeQUC9yWpl9duIjPJ7nh10c_QbLdzNmwYBHob8eSLxvdlYOB7OPfwQaMuv4Pc31tfqYcsYXbRHQnbfE_i5hmVJoEhA9nu1V2XYtWIlJax4GZPQFGhTsakA71Ta9dfU-CA--ptt0LoEWuA", "name": "Whitten & Proctor Fine Art Conservation", "rating": "NA", "id": "883a8c5ef35ab28e1630235ad65a6b16506a67fa", "job_title": "Lpc-Personnel,-Inc.", "place_id": "ChIJ8YuXE6K4QIYRn1SF1hazFEw", "address": "1236 Studewood St, Houston, TX 77008, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.3858767, 29.7300997], "type": "Point"}, "properties": {"photos": [], "types": ["point_of_interest", "establishment"], "reference": "CmRSAAAAnVpt_6o1SaCkkJYscAnZ8NHuK00TZ2mzNF7opWEeaSdJqNigTRFnhOqaqwc4rnsOTYJiM6Yobt2MpuRZLuKq2BO7uE7mIrNKTw4n4OC22pf6xcnGmgEuG86AWng1C8fEEhBvvY8kcSEA2XIiF1KFXkGbGhRlZyPqmoe0RpZsg-uioEMSXXpr4A", "name": "St Mark Fine Arts Conservation", "rating": 5, "id": "ea2d4bac6d74716b33f456dff3aae0cc0b43cca3", "job_title": "Lpc-Personnel,-Inc.", "place_id": "ChIJKbDEoXm_QIYRcRFBlp0dE8A", "address": "4901 Main St, Houston, TX 77002, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.483218, 29.7482286], "type": "Point"}, "properties": {"photos": [], "types": ["point_of_interest", "establishment"], "reference": "CmRRAAAAFzXjfe3xhY01h9bxsyBBuckD_0vd8LI8U7PZYU_qChRgHsQrvZr1Slue2Pds0cfaDkmBRxLGJNH5zl0bd_oOEdHMyhFhVTnSfC5_uXyFp20VJ6qO9D1synCvv5DqxuTpEhCxmXTyuGwJd2OzfTy0hGinGhT7Ou5aiWX8Jwz_KUc8x4EAzTIVWw", "name": "The Nature Conservancy", "rating": "NA", "id": "90af6fb9fb926dde9f7103577cebc4150bbb1dec", "job_title": "Lpc-Personnel,-Inc.", "place_id": "ChIJq-m4EX3AQIYRJkn4Lhccp2E", "address": "1800 Augusta Dr #240, Houston, TX 77057, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.42318089999999, 29.7345943], "type": "Point"}, "properties": {"photos": [{"width": 750, "height": 437, "html_attributions": ["<a href=\"https://maps.google.com/maps/contrib/106788706324997826205/photos\">Erika</a>"], "photo_reference": "CoQBdwAAAGnsjAY_5Z8ixnNRzgNNIViAYgzVQu19nfX_I64I_JOP75m_gvZF8CpQ47z_BENmdOYYDIabgACXGISsTBiirJ0nJ1PUt-_Yibvwnkof9jocOE3ZCrtz1AivhjCh_JObd7zUSu2nwonnOKFSuZnT4I-viirTpw9ZmA1MZHu-yBBVEhBVhjWWtj_WcSO0QDcIO-rZGhTuB-1LcpfnGkz7vFvMkr8gpvdFgg"}], "types": ["point_of_interest", "establishment"], "reference": "CmRRAAAA37wiGmJfCszEE_yiVW737Z2QBv4HMe78IGFjxYQ6tE5ol1GBkFY6xzb8JnDCKah4qiiETZ1GRTvegFf0pCCtxvrycsSy9ZpCuGcD7BS8CxuBC52YTpYn_uwcGVBybxq8EhAyAvktdGk7QzQ7tIjJaqXBGhQoEoNYDaITC9D_4ghmiSEQFHlSrQ", "name": "Student Conservation Association", "rating": "NA", "id": "1c5ea7722fc0d99e9f7dfca55f5d9078224d51d3", "job_title": "Lpc-Personnel,-Inc.", "place_id": "ChIJQcqBXfDAQIYRErawO-goGj4", "address": "2990 Richmond Ave Suite #400, Houston, TX 77098, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-96.038102, 30.055621], "type": "Point"}, "properties": {"photos": [{"width": 984, "height": 985, "html_attributions": ["<a href=\"https://maps.google.com/maps/contrib/110279808588468038448/photos\">Peckerwood Garden Conservation Foundation</a>"], "photo_reference": "CoQBdwAAAN6h_Me06IsNluIEJwwIJR4PRNONKHpDLTuVjgq3xyGMxeDhcPHrHsiw7r3zxsaFsu4g4eumq9wibyelEHofOrG_G_vTL1yG6n2lc7nRJoiFaW1mOVuMWq7RYal0lzWwMuFRMJIKamjQwsK0tUO6JdIzdQEbvRDWicQkV7OEirZtEhBaJq7LdJemTQMLgoPzyMpBGhSHpKutR6ZyHFX1mAwTGEaP4Scnhg"}], "types": ["park", "point_of_interest", "establishment"], "reference": "CmRRAAAAAgv_8rOQNAFBOb77nqoSVnCKyJnKiToyKxBp7GbI0XA2wcUBFy6aYgyIxW4yfF_e4DKR54shhtSuw8ZJmyZ7r1dftY_BYKo7K-NOFXQiZBSRjwsWw59b4k4ULbtkYPDiEhBCSwic9U4umg4FHol-9fAXGhS8RbORny1tvJVA8-Q6o8CeuHivYw", "name": "Peckerwood Garden Conservation Foundation", "rating": "NA", "id": "e618a4c618cd67ce4f5fdc165f640220ab3b53b2", "job_title": "Lpc-Personnel,-Inc.", "place_id": "ChIJmUR7pvHKRoYRIIl0o73bPGE", "address": "20559 Fm 359 Rd, Pine Island, TX 77445, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.64386449999999, 29.7515036], "type": "Point"}, "properties": {"photos": [], "types": ["point_of_interest", "establishment"], "reference": "CmRRAAAA2wOlsPqbviHTuvIIA1J8p0NoGG5ojVNSyzeaI9-fUx7r55iE8IuAUi_-1h8xL9WB64lxVJCpEw4jghvzLNEmr_zD5uhAuzKIuooddb3glhTRh_diX_zDSXZaW__qu73vEhDSLs1fmNAHwvuJphVQrE5yGhRyjPVTdt1jxR-YtqBZOm5prIX3CA", "name": "H2O Conservation Technology", "rating": "NA", "id": "30c07988ef8dfc62dac712b9d587daa4a36f2539", "job_title": "Lpc-Personnel,-Inc.", "place_id": "ChIJIWZRKeHKQIYRXxta3wOMGGc", "address": "1725 Hwy 6, Houston, TX 77077, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.5705632, 29.7714443], "type": "Point"}, "properties": {"photos": [{"width": 3024, "height": 4032, "html_attributions": ["<a href=\"https://maps.google.com/maps/contrib/108143329814504597326/photos\">State from Jake farm</a>"], "photo_reference": "CoQBdwAAABTNrnj7g3t1q78PntvwjS__yzEeNrAmp40iXmYYM7BLMyXp-mmZp-53JLp5mUh5vXHVulH9uQWKm0_fkplBwlITthFFY4A4DK8a2FeAMgMY4GXba8DcBxqmtdRUteq4_qC3sfgCjxX0PlnPtOb6-iXCSge9r4XR26h6IA2bDapAEhDdkS-W0QZ-_mKnnNnAK2KxGhSJXs7h4Llc3ck8zPmyRSlRM2L3bQ"}], "types": ["park", "point_of_interest", "establishment"], "reference": "CmRSAAAAhXo42Z7G307700tMcTOuKMF3B4g6NHNBnJeFlnafOHHgNhQdyGqg5TAuUCfoqrs5fWgFu-3eHtQ5chCxVNoy_TVCiaAziP3gjdfT3sNP24bbk4ebONfncWBN_-n-kX9qEhBfmHtU6Ll6O0LjPYPUeceFGhRENVbwsVL3ilfcOfaDhyBQVz9FXQ", "name": "Houston Audubon Society", "rating": 5, "id": "050a5458d86bdd1cee7b09678bd6256d0a20a73e", "job_title": "Lpc-Personnel,-Inc.", "place_id": "ChIJlQOxwVDbQIYR2uX_TZl0TYc", "address": "440 Wilchester Blvd, Houston, TX 77079, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.56820189999999, 29.770778], "type": "Point"}, "properties": {"photos": [{"width": 1800, "height": 1200, "html_attributions": ["<a href=\"https://maps.google.com/maps/contrib/108765250995932379967/photos\">Audubon Docent Guild</a>"], "photo_reference": "CoQBdwAAAAjgARnA7i1RESHGhKNBb5CMrGtTNmu-DwOw2Swm2QcaVsMxMS7QsMPocnPsW263IhRfgCbFx9cZTJey0x4QiyGWd16H8USwqiw3PoXOqjciCta4ywU0_VKh5RsDo51BLC9QlS_wFzdbFIXL_nJMR-gcMyuf2EhT09HC5xpE0C3ZEhDQ2gcRSkLGVnvc3MZXIHw-GhRcT62T2HDjdsP_fJ48lhQM_ZMMEg"}], "types": ["park", "point_of_interest", "establishment"], "reference": "CmRSAAAAlG884QpWIR_J7BLDN0hUZMeisPhpZjY_ZKrhrbcp8peAD6cQ6uubRm-kDSK9zUkRUA0-MdP-FY4PwvM2657qKx5L88eQ0m_6sgAeV7w2cDyhX1lG_VODUK49glt-BNwQEhC5rz1MqbQd_l3qHJIbimzjGhTZmuAUvvcjSnKZ-lnWjX3JiulmDg", "name": "Audubon Docent Guild", "rating": 5, "id": "7ddd5daf76cc4979e2ba6b062322d1c77d5d1c07", "job_title": "Lpc-Personnel,-Inc.", "place_id": "ChIJI9XyNFHbQIYRtwHb8EtTpeU", "address": "440 Wilchester Blvd, Houston, TX 77079, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.44932349999999, 29.7803218], "type": "Point"}, "properties": {"photos": [], "types": ["point_of_interest", "establishment"], "reference": "CmRSAAAAS9cAhoKZ4njxctv8RRXfMNVWbOMmr7m4B6RqAG71QNSAYBK9q3uHF_YOvyFSW8Bs5nIVoCFV4FSoNFBYGA8kGV2WeIqwWv5Saw_QONExcwXSQXg86T-Q7081KPlZbe--EhCAeKATNN9_rEdINolfPpDbGhSCp45gUzEv2Ul_EYIJSesi0LH7Lw", "name": "Coastal Conservation Association-Tx", "rating": 3, "id": "7258b034e119f31e82320bca6e72781ee9f79d75", "job_title": "Swissport-International-Ltd.", "place_id": "ChIJcekacM_GQIYRPzL13cgQrPk", "address": "6919 Portwest Dr #100, Houston, TX 77024, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.47039, 29.655454], "type": "Point"}, "properties": {"photos": [{"width": 5312, "height": 2988, "html_attributions": ["<a href=\"https://maps.google.com/maps/contrib/101184977609161362375/photos\">aug4</a>"], "photo_reference": "CoQBdwAAAM_ZXW29wRyw3vW9RXu6SDC7Gl2YlhsR6GQ-tI72zJXeZs4cjXZhU4nTqHdVb0MW3WxwtAkJiMPxEiG6bux7m8WuHTAd-LaFPs93t4LnZhs3c4nG0LRon0yqNMjXWUmJjYhWFz8edIM2Hj-n7xx797vpg25OhXTX9JCJZIXK2UyzEhBUueqG0M4mUHI_1anuD4Q8GhRvlImQD0N5lLJ9WLMKixvAuziNGQ"}], "types": ["park", "point_of_interest", "establishment"], "reference": "CmRRAAAAaIlHr5h3mLWwdcixzKByyma2aot4JxTF-sEClf-NN8N4eeG6nEOGssHiJtpigI4tCcnztZwTeJhqb-2h8cd4IildBOtn3142eRmbeN1bRTn4K97mhibvT0dy26NwPqxMEhCOp0n8QuFzi7jAWL2ApiITGhTUO98rg9jCpIq7Ik-dLJJhg58YEg", "name": "Willow Waterhole Greenspace", "rating": 4.3, "id": "0127506e8071350c2d48f0ca56e939045297a0f4", "job_title": "Swissport-International-Ltd.", "place_id": "ChIJR6_2zTzqQIYRsA7wExgfDWs", "address": "S Willow Dr, Houston, TX 77035, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.4003322, 29.7388505], "type": "Point"}, "properties": {"photos": [{"width": 1136, "height": 640, "html_attributions": ["<a href=\"https://maps.google.com/maps/contrib/117056878997299689379/photos\">Marisol Brown</a>"], "photo_reference": "CoQBdwAAAOkXvhTLjcDqzdv7i1KJLiDQNoEmGB__S9GFg9kufZO80M7Jfj9lG724wYqNASqv5sAKHRMYp64LHdoQ9PmM6-mTlYaXvZBmmHm-yuEw2d0BFULhkg8onj0FiSixtytb9c90qXijIZ54mpl2N_OaiVc2qWXFpfEOZan7pKJIN99pEhAQc49t7W4RDJQwBpsHcdroGhSzh2vY30wfBphZCamgKQiYjGR_9A"}], "types": ["point_of_interest", "establishment"], "reference": "CmRRAAAAvna0jrgMiIZKG0Sbb_WwxcnjwWijXYjHwtE6Sj8vTssxXWFd3yn5W3YEijJh3LD0WwCzShZD0QRm8q22Li-wrM54zf4WprTy19Wy_84tF8z7v3BYaguJJYwdUsQo3tIsEhBAyg1id_Y25_QGKQ3aBxS7GhRcq_7wV_7VPUjLzma3E37VGlkAWg", "name": "Masters Fine Art Conservation", "rating": 5, "id": "a462c2eef4e22ea319485ae7b84f3d20756cbdd1", "job_title": "Swissport-International-Ltd.", "place_id": "ChIJp8u2bZvAQIYRbosnWz6cVmY", "address": "1612 W Alabama St, Houston, TX 77006, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.3876169, 29.794149], "type": "Point"}, "properties": {"photos": [], "types": ["art_gallery", "point_of_interest", "establishment"], "reference": "CmRRAAAAAVLJB-tgYVqqOxVbxyMMGGbVunMTBkwarseIo89xa1dtly52elJXzb9DpOxdImsssbEpiIGEmxoMH3P2YuHepjnBSPh2GlSjpQsaqUM1kguA4XWGaDpfbTWdEFXruNUhEhAEd36A1h4jnxE8oOlILfbcGhROSUYq1MCvjjME7o7pYsiMFbA-sQ", "name": "Whitten & Proctor Fine Art Conservation", "rating": "NA", "id": "883a8c5ef35ab28e1630235ad65a6b16506a67fa", "job_title": "Swissport-International-Ltd.", "place_id": "ChIJ8YuXE6K4QIYRn1SF1hazFEw", "address": "1236 Studewood St, Houston, TX 77008, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.3858767, 29.7300997], "type": "Point"}, "properties": {"photos": [], "types": ["point_of_interest", "establishment"], "reference": "CmRSAAAAuX9r6kaAE3OHwnR_q6ZnAS79tNmgDNzU9KQ-6aXywjWG6gd08rViODIF3-b_2zDWvkA83NGOEOCxpUkZEs7AiCpIf8G3a5k-Sz5CsiyxTgIkwSfJZi4ynNi7EsGg71oOEhAGWJvAWicYnIArCf-zMTH3GhQJlO1TwKZZkoFMADHS2f5pwNrmBA", "name": "St Mark Fine Arts Conservation", "rating": 5, "id": "ea2d4bac6d74716b33f456dff3aae0cc0b43cca3", "job_title": "Swissport-International-Ltd.", "place_id": "ChIJKbDEoXm_QIYRcRFBlp0dE8A", "address": "4901 Main St, Houston, TX 77002, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.483218, 29.7482286], "type": "Point"}, "properties": {"photos": [], "types": ["point_of_interest", "establishment"], "reference": "CmRRAAAAzKFQM6KBQrsMSAeLD5V44pLZRdR5KHKZ-A606wjsaARL3yYx80-MvobNbPzNt8HseSvsrljLfrOdu1HpNIC85b2BXR5dweAVdQh8MzbN_wcHJhEWOacXTpQplL7L2jMzEhA8PV6BLe-qaIeohRuZQpzWGhSqu-ebSsgQ2dOZ810JZ1DjxUjuKA", "name": "The Nature Conservancy", "rating": "NA", "id": "90af6fb9fb926dde9f7103577cebc4150bbb1dec", "job_title": "Swissport-International-Ltd.", "place_id": "ChIJq-m4EX3AQIYRJkn4Lhccp2E", "address": "1800 Augusta Dr #240, Houston, TX 77057, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.42318089999999, 29.7345943], "type": "Point"}, "properties": {"photos": [{"width": 750, "height": 437, "html_attributions": ["<a href=\"https://maps.google.com/maps/contrib/106788706324997826205/photos\">Erika</a>"], "photo_reference": "CoQBdwAAAPA68PhD7RL9NUnlOocP7D5LdYfSSWef-FUV_sNID8ekvTIOgzbtsjJmgbtUH28_T1r5ipIdI7TGpww9XyUBrbcF2Tok5k6HnbNut0OMX5M-yskN0lPVSmnR_tcyFP0pKv1qopI3Ebv82dN_uyDz2jaNFgS68WlXC8HrCAxbq7CmEhAgxQ6GSRbV23sco5dSwOCGGhQmEr5s-oS9m6TSdMEFpdPIHJiOVQ"}], "types": ["point_of_interest", "establishment"], "reference": "CmRRAAAAMwlOEgsc49s-lQyPLPZlRZnDR4HB_gPTxq0WjHhEyXdy07MjcaqhDFPj0GZyO3Mjb47D-RynxdPYHWRBKfuHm97rmZ0rFZStgt0YOwnBZu1XQf0o4paoHccH2AJkY7lyEhA4cDtUr8n69BtkHkvlhAlUGhTBWCJnt3YTgZoVJlnZJ5vEXde_iQ", "name": "Student Conservation Association", "rating": "NA", "id": "1c5ea7722fc0d99e9f7dfca55f5d9078224d51d3", "job_title": "Swissport-International-Ltd.", "place_id": "ChIJQcqBXfDAQIYRErawO-goGj4", "address": "2990 Richmond Ave Suite #400, Houston, TX 77098, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-96.038102, 30.055621], "type": "Point"}, "properties": {"photos": [{"width": 984, "height": 985, "html_attributions": ["<a href=\"https://maps.google.com/maps/contrib/110279808588468038448/photos\">Peckerwood Garden Conservation Foundation</a>"], "photo_reference": "CoQBdwAAAE6Loq5rxN_vt37bzlZ2DP15yfvD8X-dhp61sjdRQbqckODByP_gaK13h5heXbSV3M9JORFr08isaldY5wmwWDVwHVPy2XXH2_RQE15aHkLGh5fcai7_cLW497xWd_pb-iLTlYl30EXW2ZdC7_lF5GJEaxsNADo3yNjxUl-pkwicEhDQ6aq_R8Ge0rpQqQ1lb4PtGhThpX0ebIEmirDm1J__kiancSlmTA"}], "types": ["park", "point_of_interest", "establishment"], "reference": "CmRRAAAAQPC0P11SW4c0tFdmPspankV_B5qtoRf9w5vFh5wJNbz3SEAR6cNxVzIVDQWrigxG6efhGotVzsljeyCr2r16heuGwN-5lNMmyZ6wvF1IsWac9kU985DdLlnZ_tZ7lVa3EhCFeRM-80u382ycYstipV8_GhRbxslF-ierFiu8g8wvpIQDe26-KQ", "name": "Peckerwood Garden Conservation Foundation", "rating": "NA", "id": "e618a4c618cd67ce4f5fdc165f640220ab3b53b2", "job_title": "Swissport-International-Ltd.", "place_id": "ChIJmUR7pvHKRoYRIIl0o73bPGE", "address": "20559 Fm 359 Rd, Pine Island, TX 77445, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.64386449999999, 29.7515036], "type": "Point"}, "properties": {"photos": [], "types": ["point_of_interest", "establishment"], "reference": "CmRRAAAAi9s5Ns5drgOfVjw60IyEv_P8hcsJWoy1zA1HZq2WAF_-_82ICxWpQ7W6vxCJlbNoZwvNBneHab0HiiRmuE_auKWHbNRc1Be9EaGPI_aKzXi7t47TjTHHx9p0jyQ0sXG6EhCk0e4AI_cioJGz4I7Mk-fRGhTskdmr6rBKgkdMgcAD2ie3lZvZpg", "name": "H2O Conservation Technology", "rating": "NA", "id": "30c07988ef8dfc62dac712b9d587daa4a36f2539", "job_title": "Swissport-International-Ltd.", "place_id": "ChIJIWZRKeHKQIYRXxta3wOMGGc", "address": "1725 Hwy 6, Houston, TX 77077, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.5705632, 29.7714443], "type": "Point"}, "properties": {"photos": [{"width": 3024, "height": 4032, "html_attributions": ["<a href=\"https://maps.google.com/maps/contrib/108143329814504597326/photos\">State from Jake farm</a>"], "photo_reference": "CoQBdwAAANrr65Hi8dqhIJ5ae8n8kF7ixo5GOQgpOe3GaqEoIU7TpZV_mqGl3RBj91eeXhTFamxhcRfHjC803ZqtlQD8FJ3_cFegF_d07GDQebrlOBrBdTwSnU612T5CSQOi0tRgUfMQyOqPE0WDQoLJqypyMAv9fqZ-iC9xcl_E2kdIDynWEhA_ATBign6fwz0o_k0MFr8ZGhTm_D_NiFHVkfWhPlb_2U8j3dnz4g"}], "types": ["park", "point_of_interest", "establishment"], "reference": "CmRSAAAAEaIjo1g4GM1wkS7cBH1KpuHY8KH2oVgpMaZmAnLZ-JfkpAgZ6IsYd4fyTS8ZYYh3GeFGTqjGZyOHaITWdAUtV874s9RuBh6dMNgC0GNo2HeJ7vtcXRI3vRgXSahyQmwmEhD4XBiUKFnc4KGCWN56g22QGhT60iITjp0kKicCxdf0eHvS3_R-kw", "name": "Houston Audubon Society", "rating": 5, "id": "050a5458d86bdd1cee7b09678bd6256d0a20a73e", "job_title": "Swissport-International-Ltd.", "place_id": "ChIJlQOxwVDbQIYR2uX_TZl0TYc", "address": "440 Wilchester Blvd, Houston, TX 77079, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.56820189999999, 29.770778], "type": "Point"}, "properties": {"photos": [{"width": 1800, "height": 1200, "html_attributions": ["<a href=\"https://maps.google.com/maps/contrib/108765250995932379967/photos\">Audubon Docent Guild</a>"], "photo_reference": "CoQBdwAAAI9Kwb-WSaNfpGDmHJjlxX1UGnFoZqNeHAR09IyyXnxTWco5v_vMvnjdFKjuFtsC6PJh-n4UWFWR-0QvgWvDGrbnZsqmnFAfs9B7dUlXHa7lhxbHG_qlstQ9cLOznBKGWyGVRWBxTx0IBfJ7xe_WVi-OhLNJUtkWa13t0LQVuXn9EhCblEV5lMdr-5OvLyN_a1JvGhQBlZMYk7qNAlpW0L6CLn1_AbyTiQ"}], "types": ["park", "point_of_interest", "establishment"], "reference": "CmRSAAAAHdcEVbVKLnY6suEC-Om0j5wWH3tQabHpBotwseDgxI-FC-bfmAqxNpoyV-P3qo5N0_jdmxm3ZdNZN0rmiX8_NV0ClXezIUvCvCJSv4_3ZFFJgZrfUk0ZZ4QncGPSFDy3EhCeISi_PLXn6x5FIrZxO8zNGhS7vqZSmpNCRZHmd7zgAS-5Jqmjbg", "name": "Audubon Docent Guild", "rating": 5, "id": "7ddd5daf76cc4979e2ba6b062322d1c77d5d1c07", "job_title": "Swissport-International-Ltd.", "place_id": "ChIJI9XyNFHbQIYRtwHb8EtTpeU", "address": "440 Wilchester Blvd, Houston, TX 77079, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.44932349999999, 29.7803218], "type": "Point"}, "properties": {"photos": [], "types": ["point_of_interest", "establishment"], "reference": "CmRSAAAAvZ1XwZDt3_BZdUV5B0OcM_nGzejKpC2lPkvR9H7hSrPObCIYfRKGUnGfcq9rxxDZg3bGwYQaICjJJpoXk4pYwOh80BIEstafkW7ZgBKDTnUbItMfQhVxf3K0YtIbQiz7EhC85cCiZsre10wrhsJVdD-CGhR9gWz0vH5lS-UzcNYvpAcneX3SVg", "name": "Coastal Conservation Association-Tx", "rating": 3, "id": "7258b034e119f31e82320bca6e72781ee9f79d75", "job_title": "Kindred-Healthcare", "place_id": "ChIJcekacM_GQIYRPzL13cgQrPk", "address": "6919 Portwest Dr #100, Houston, TX 77024, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.47039, 29.655454], "type": "Point"}, "properties": {"photos": [{"width": 5312, "height": 2988, "html_attributions": ["<a href=\"https://maps.google.com/maps/contrib/101184977609161362375/photos\">aug4</a>"], "photo_reference": "CoQBdwAAAJqkoDSiArcNbqDVBWfH2Wz1z_5Md0hDdhykSl6mN3a3ficHIbCHhFQFTH9HvCIIYIcSAX018DtUd97NQT_9BNeXdcXzl2J8paM53fhsnzjgjxhEH8GHp52jS9IbSceqixOIC0Tl-WJYuwh2GB3H795pkuM8pCAd_XYsb-dJx0K2EhCm9_m4vCxTrmuiuKYeb-wQGhRMvBDnAXVw6ZiJiQ98Y-O8valSNQ"}], "types": ["park", "point_of_interest", "establishment"], "reference": "CmRRAAAAzipNb7ZUf49GPhsKm5A2CLVM3bAa8EKFYd6LFNi4eNnQCpZY3sIgn7TTbUnl7r_8OBNT8vuEDdtx7Y9_CFoYgnYOioDIDM4D0xXi73eEsPDEESr6xry89JJS4haNYhZJEhDnmCOcyXucOUwNmlYERJfeGhSCSYQsNGF2VubxXvIwMGYx4CaMNQ", "name": "Willow Waterhole Greenspace", "rating": 4.3, "id": "0127506e8071350c2d48f0ca56e939045297a0f4", "job_title": "Kindred-Healthcare", "place_id": "ChIJR6_2zTzqQIYRsA7wExgfDWs", "address": "S Willow Dr, Houston, TX 77035, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.4003322, 29.7388505], "type": "Point"}, "properties": {"photos": [{"width": 1136, "height": 640, "html_attributions": ["<a href=\"https://maps.google.com/maps/contrib/117056878997299689379/photos\">Marisol Brown</a>"], "photo_reference": "CoQBdwAAAB82K83scX5vicejjCl5LPWO-dZfnZNVMVSKexOH70yHpL5ooj8Wt5X9P0iTG7iLe5r3xVfavSPk4rlCOSNFpwnS55QBJUDWMSrR7i-QLhWdfnlYawxXd3JD8CuEe6koi1gvcv4Imq_8H6d_945wVi2OZxOaOV_MdLwADsxBDpnFEhAP-rJVOdkVvHyGvvsiZtf7GhQC7Ys3Hhw1ymxeGsQLABu5LuPW7A"}], "types": ["point_of_interest", "establishment"], "reference": "CmRRAAAA82PzY37OiGXNomP7NhDEOJ6oR6w9jpsoBsD4gEqgizicIzR24Omp7lDU4pQHaYtAw0O7HFc80ndB9--hESwmZldYMr3SIomjpaMd0uGoOvgYXYr95gIbD0ihHuxOYWsjEhDAvP6ouEHAXqkxjogII3bfGhSuUCDRXyqiJmiH3Be2nqFGE7-XSw", "name": "Masters Fine Art Conservation", "rating": 5, "id": "a462c2eef4e22ea319485ae7b84f3d20756cbdd1", "job_title": "Kindred-Healthcare", "place_id": "ChIJp8u2bZvAQIYRbosnWz6cVmY", "address": "1612 W Alabama St, Houston, TX 77006, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.3876169, 29.794149], "type": "Point"}, "properties": {"photos": [], "types": ["art_gallery", "point_of_interest", "establishment"], "reference": "CmRRAAAAA4iu5dflH6MdEmnMT5uoiXVMCSYYegwqK7j9JxGAjyXA643ptQlXbJhuywoyXDB8pxG9mGidB1guu-c9DG6n6N9MnjK621Q9f66FN1wdLxN90hPYvmSfFJBebj-iEtLKEhBgWxeZQtJFW2Uobm5tLTC4GhRDN3GDSI88axsUwlvJdnExLgw6HQ", "name": "Whitten & Proctor Fine Art Conservation", "rating": "NA", "id": "883a8c5ef35ab28e1630235ad65a6b16506a67fa", "job_title": "Kindred-Healthcare", "place_id": "ChIJ8YuXE6K4QIYRn1SF1hazFEw", "address": "1236 Studewood St, Houston, TX 77008, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.3858767, 29.7300997], "type": "Point"}, "properties": {"photos": [], "types": ["point_of_interest", "establishment"], "reference": "CmRSAAAAA9CJv6wsPUvPGSNBcCIJGbsRbMAK8x9I-OZRljlbuU9fKBb8JmdnBWeh7YFkS3OwwM3EyZ51XyL-vXByCr1PbJlwMYIeWk3hNrwfv6spP8QkMfGLcAYNH5WAFVLfCT_hEhDCUi5n_ECwWdDIveiNCBFgGhSybqiRbeODHGalRiqltaBs_gGsMQ", "name": "St Mark Fine Arts Conservation", "rating": 5, "id": "ea2d4bac6d74716b33f456dff3aae0cc0b43cca3", "job_title": "Kindred-Healthcare", "place_id": "ChIJKbDEoXm_QIYRcRFBlp0dE8A", "address": "4901 Main St, Houston, TX 77002, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.483218, 29.7482286], "type": "Point"}, "properties": {"photos": [], "types": ["point_of_interest", "establishment"], "reference": "CmRRAAAAWypVaw0DZU5Xqpu_RFDoyTbT0W8PdJl0OuJS7GaoZeQKOaMcRLNQGxg8OURJ9Csn5VSTcaDJ5r0HW1RubwjPQCukdCYURiZkNIeA8esQ5GLphs_VkF3TKtveJAK0of0QEhCyUvPVF-hQK65ZT9_N_sSTGhSIHZFWcsWvfUMfg_lOPlAPo-H6kg", "name": "The Nature Conservancy", "rating": "NA", "id": "90af6fb9fb926dde9f7103577cebc4150bbb1dec", "job_title": "Kindred-Healthcare", "place_id": "ChIJq-m4EX3AQIYRJkn4Lhccp2E", "address": "1800 Augusta Dr #240, Houston, TX 77057, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.42318089999999, 29.7345943], "type": "Point"}, "properties": {"photos": [{"width": 750, "height": 437, "html_attributions": ["<a href=\"https://maps.google.com/maps/contrib/106788706324997826205/photos\">Erika</a>"], "photo_reference": "CoQBdwAAAIDYaJHL9Rk2d7l6AHdPdywRaVMrJPYYvMVn9eZvm2_fpAxu3Y08WX5Q6Y52y3lhW01vQDhm7AC-69yMwnfBLGEvnLogJQroKyrIidmZSfiRBnsHwyvWdJypncO2U66GwpXRQnAN5w60fuSopJGc56Y6YM74kbqgRi60YJ3TJh_tEhCwibyt6oTh4Vda8fnXJuB3GhQtuy3VUISTQDKVPej1AtmuFqCIsA"}], "types": ["point_of_interest", "establishment"], "reference": "CmRRAAAABBe47gL9H3Ls_vgIuX7QVQo8PYkznNOUF73KWd9oFu8GP-PIQGAtsfgeLc59I6Ip6lAryjj33zRJ78SdbO13zentmst6K7JQGSdQ9L7m5CFaReznnhhmU7Aww-FU4f9UEhAofQ9Tp39RLnnTIBLvf8AgGhT6tz9Za9jnoDx2naeTV9uZYY5ISQ", "name": "Student Conservation Association", "rating": "NA", "id": "1c5ea7722fc0d99e9f7dfca55f5d9078224d51d3", "job_title": "Kindred-Healthcare", "place_id": "ChIJQcqBXfDAQIYRErawO-goGj4", "address": "2990 Richmond Ave Suite #400, Houston, TX 77098, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-96.038102, 30.055621], "type": "Point"}, "properties": {"photos": [{"width": 984, "height": 985, "html_attributions": ["<a href=\"https://maps.google.com/maps/contrib/110279808588468038448/photos\">Peckerwood Garden Conservation Foundation</a>"], "photo_reference": "CoQBdwAAAMepmQiVye5X56eHv6tiROfrNyrVss9zqx6SqRY_dDQadgL5wj4kxNBY1W-hRxGHKaE7kHlAcsPRtn-sctRtluEZu0hxN2oucujKsJ4qIfAUQ2fyIahmuHIiZP2Zx4HNQgfBZZpbQGZh9NJzcCrKLO-dW7gntf0IrEphb1I5g4nnEhBFuGtohXFmoTGFRs0RB3WbGhQyX-BjlnRMe-gkQGFGRp3EaKQbcA"}], "types": ["park", "point_of_interest", "establishment"], "reference": "CmRRAAAAKFwj56q32D57KHfJem1LGWFZibwW2I2TiH36Z6yz7BmgDLkZxWQ58eSn0BxjX7x4sCnYhuC1aYKDVw06GX7m966Mq8m5vqCQsZ_oNiqm0ZWI_tCDl1-JcN4puZGdhbCnEhC1wBUxpX4tj_mto3NJZYeSGhS71pDIircmhdM5YrWMRFdJ2QeGWQ", "name": "Peckerwood Garden Conservation Foundation", "rating": "NA", "id": "e618a4c618cd67ce4f5fdc165f640220ab3b53b2", "job_title": "Kindred-Healthcare", "place_id": "ChIJmUR7pvHKRoYRIIl0o73bPGE", "address": "20559 Fm 359 Rd, Pine Island, TX 77445, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.64386449999999, 29.7515036], "type": "Point"}, "properties": {"photos": [], "types": ["point_of_interest", "establishment"], "reference": "CmRRAAAAs-91qDB1GcYMtzs7guexq5fRvtxtQpAwJh2LqLOlLa1FfY801OMlsgFX78FLFTl4sfKaZWuILwXr6g2MVVjQQ9EZCs_EzXih-jB_sDOErCx9k1aV1FMq-eJ8uROB-1H8EhAZgf1eRdJPsBjQd4MYqxq_GhTQZwzRXWfs0OHb2HTvgMSpf94HCQ", "name": "H2O Conservation Technology", "rating": "NA", "id": "30c07988ef8dfc62dac712b9d587daa4a36f2539", "job_title": "Kindred-Healthcare", "place_id": "ChIJIWZRKeHKQIYRXxta3wOMGGc", "address": "1725 Hwy 6, Houston, TX 77077, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.5705632, 29.7714443], "type": "Point"}, "properties": {"photos": [{"width": 3024, "height": 4032, "html_attributions": ["<a href=\"https://maps.google.com/maps/contrib/108143329814504597326/photos\">State from Jake farm</a>"], "photo_reference": "CoQBdwAAAG6SgoN5ktX6SFw68mhYAKd29OL0cEqkQ6tvH74tfKBMDqzkpm8I6VRtsuPEhX5S4lCI-gUDnKUg0hHANBhGcbpOKbilhiRZBZgyusbI2JQi1qHvQsL-DWrcFedYg6z_zqVb8DA5sVk5DNewAW94jGOD2pJEiBfy0nW1m-c57U9BEhBPK0DbsMbC_BQmI2OZ009rGhR6mnvzr2jQhonzVEC7bV2qT1WBpQ"}], "types": ["park", "point_of_interest", "establishment"], "reference": "CmRSAAAANjTY4ngQ8fabAFYRP5ApGNI_R2iCAAzokyEmVfIgfhhAu74aclwkqRR5vvIWMD4EFO16U4JPvn3_uMAGD3ioaD_4rVoAuYsv7GCjyJMy2c6R4Xr63EhQFa4JeBYNkU8fEhAhF35MARcUNkN19F3W-hpcGhRpLO0y-FB7cp9n99lMXF8ftnh1yQ", "name": "Houston Audubon Society", "rating": 5, "id": "050a5458d86bdd1cee7b09678bd6256d0a20a73e", "job_title": "Kindred-Healthcare", "place_id": "ChIJlQOxwVDbQIYR2uX_TZl0TYc", "address": "440 Wilchester Blvd, Houston, TX 77079, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.56820189999999, 29.770778], "type": "Point"}, "properties": {"photos": [{"width": 1800, "height": 1200, "html_attributions": ["<a href=\"https://maps.google.com/maps/contrib/108765250995932379967/photos\">Audubon Docent Guild</a>"], "photo_reference": "CoQBdwAAABsJvYup_nQj5n-W_DF5yGak0QwY6qi55AIcq7wDxoDbQNV-NVu5Jf6qCTHtr8XTLwqqLKIE8yFzkfAal2qV8sUgKT9FvYUm0cCjC9XIGAmITDWh2XstnxvGybkZe8HeBqbNMk3NElDU0V8wQ38JBUqwgOePNweMTcRJINw8dduPEhCr_PWqButqSDUaB2LE8IpfGhQauZLro1IMdXd05ip0-POC_sOJBQ"}], "types": ["park", "point_of_interest", "establishment"], "reference": "CmRSAAAAjwtePYyyysNaJ_NhH8fxHu2zVCF4CprI3-GC3jcrUiIZdcVLUCCi_L22Gl9gpR3lZCigjJ7vo_TTZudyvniV3sPLRkmfQuRwMa8QxYMFPsfuxYgPIb5ufyeocq3DzmrcEhDeoAtCqRmykjgCRvSACtGyGhTzwHC7_8YCt5gkIXnaNvrfLMjShA", "name": "Audubon Docent Guild", "rating": 5, "id": "7ddd5daf76cc4979e2ba6b062322d1c77d5d1c07", "job_title": "Kindred-Healthcare", "place_id": "ChIJI9XyNFHbQIYRtwHb8EtTpeU", "address": "440 Wilchester Blvd, Houston, TX 77079, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.44932349999999, 29.7803218], "type": "Point"}, "properties": {"photos": [], "types": ["point_of_interest", "establishment"], "reference": "CmRSAAAAetob3rlER0zdTUjI7i66IbvdpECl6fK78P3c-Ts5oSe9Hahwe9IaRckiTEW-lVWKeLMwS3bFIkQ33FzSDRXxNZrIS6Z_OcLy8OKYwi65PvdPB17YO8wfu_b52ZN02FhvEhD2esYkyt-Zsa0kNSJFmaDlGhR5xInuvwujJ2gd1ooGHWugOc48sg", "name": "Coastal Conservation Association-Tx", "rating": 3, "id": "7258b034e119f31e82320bca6e72781ee9f79d75", "job_title": "Select-Search%2C-LLC", "place_id": "ChIJcekacM_GQIYRPzL13cgQrPk", "address": "6919 Portwest Dr #100, Houston, TX 77024, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.47039, 29.655454], "type": "Point"}, "properties": {"photos": [{"width": 5312, "height": 2988, "html_attributions": ["<a href=\"https://maps.google.com/maps/contrib/101184977609161362375/photos\">aug4</a>"], "photo_reference": "CoQBdwAAALjzb3u5fX8pQEQcVc-ihlMp0uXbA9_ooCWakfEgUk29wS8W7OdAjaV6K7u2vs6G1uunfzksVwIF2dGMq2THapPBNSQRKcVLeatI2P57zGSdhzR_Tm0hiaY37LPvXcAiz4tZluSTemEQQ28OHCmxHWIylMEPg_I8PS031fFh8AaEEhBZzevwEc6pzUwZOpoNFNtoGhSnjK188KbRgSY9J0PSrh67ArQ5zg"}], "types": ["park", "point_of_interest", "establishment"], "reference": "CmRRAAAAH4zoYogrApLM6nCmWeHMDDNsKKC20B2hPLJW9gXsWroOrwPcvrzkC3ZlEozqnavLXOoagkrj7AefMtoKuEBIo5CR39xDopPBJaNzVrH0tLXzvpnqlds9dHrzvXilvyTZEhCEGdpfH4vZavujHBbW7iFOGhSzul6qToJBco5a4HtGYF-zM39Dhw", "name": "Willow Waterhole Greenspace", "rating": 4.3, "id": "0127506e8071350c2d48f0ca56e939045297a0f4", "job_title": "Select-Search%2C-LLC", "place_id": "ChIJR6_2zTzqQIYRsA7wExgfDWs", "address": "S Willow Dr, Houston, TX 77035, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.4003322, 29.7388505], "type": "Point"}, "properties": {"photos": [{"width": 1136, "height": 640, "html_attributions": ["<a href=\"https://maps.google.com/maps/contrib/117056878997299689379/photos\">Marisol Brown</a>"], "photo_reference": "CoQBdwAAAKwl7vnskOGqA3p05PS1Out9GT0hKoYmoHySQtSAK1TfPeLqd_8nrKDSm4GqjOsxB1TqlAS0I1pmGqXjmjMKZiyfOlGHXXCjBTyGAXKSOmptJzt2evBkeMIaRbuicTUCRpKLLWdbMNIFbxMHbcAJtYJgLha3wekoJ-ajJtb50a4-EhBv2HlywTeeQvSE8SOWXPrxGhTHf4PfPNTyJa4JL_Re1CHHex5rnA"}], "types": ["point_of_interest", "establishment"], "reference": "CmRRAAAAVkR1Zmef9OW80OhiAQRSUy-Ym3rMOUUc7nCHeVhws1XstAVKvj89221Oru1CWCsjkzHu9xM2h8qA0Ivf5PHH0x-wqM_2uoNOwfQSAaa0xQNWOztWaNHfyE6t9yqz_wUEEhCHyc3ucEw6W6VTq8qFhuRjGhR9t7oYtkDflBxiVxrG_j-Y_USkcg", "name": "Masters Fine Art Conservation", "rating": 5, "id": "a462c2eef4e22ea319485ae7b84f3d20756cbdd1", "job_title": "Select-Search%2C-LLC", "place_id": "ChIJp8u2bZvAQIYRbosnWz6cVmY", "address": "1612 W Alabama St, Houston, TX 77006, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.3876169, 29.794149], "type": "Point"}, "properties": {"photos": [], "types": ["art_gallery", "point_of_interest", "establishment"], "reference": "CmRRAAAAYY92Ajbjk6VZRV7x0VEI7H0xckzM1hYPuEEJFWVp4IsJdvZy2VPkmJnqHBsDsDBfBorvwchDzL9BC95VB9OqJOIWDqoZLtNnAnzUoP4HE4SMRctqKYgAoLVIz7IaJN1dEhC5LEbH2gbgCGw6CFfjWgn4GhRedcikQO23vpukYVLOvRGXMjDnsw", "name": "Whitten & Proctor Fine Art Conservation", "rating": "NA", "id": "883a8c5ef35ab28e1630235ad65a6b16506a67fa", "job_title": "Select-Search%2C-LLC", "place_id": "ChIJ8YuXE6K4QIYRn1SF1hazFEw", "address": "1236 Studewood St, Houston, TX 77008, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.3858767, 29.7300997], "type": "Point"}, "properties": {"photos": [], "types": ["point_of_interest", "establishment"], "reference": "CmRSAAAApzQaUQtxlDP_pAzkQKGnf_HNMzPmEmEmBXAd_o79dlP98KFdzCLVRkqEENTzQIx-EqtUUchCxY709kiA8giti-HGo6fvOASrZAAs5kiYeGYjLOvMnsLj4TqT2zPyeaGcEhA9c1aHxxWsro7y1b3Pz4vQGhSLIu-1l5yKrisuX1e5FZby0Ilnqg", "name": "St Mark Fine Arts Conservation", "rating": 5, "id": "ea2d4bac6d74716b33f456dff3aae0cc0b43cca3", "job_title": "Select-Search%2C-LLC", "place_id": "ChIJKbDEoXm_QIYRcRFBlp0dE8A", "address": "4901 Main St, Houston, TX 77002, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.483218, 29.7482286], "type": "Point"}, "properties": {"photos": [], "types": ["point_of_interest", "establishment"], "reference": "CmRRAAAAS5Cv_-8JJA5iHqZeFXt3KGV0Wqbtz2964jl9q15kNTUGCPETP4_U5LINjGKZePreNn8Drvge_m8dX7-HJk8Dh1mdAldDepLpSCR8jOYD-uGTNf6Em0a15Z7xXQNWccKQEhCNwfWy1I3xHgTE9q8qcsoAGhR6wSvuoHCTGwKICGToN0uaWlMRrw", "name": "The Nature Conservancy", "rating": "NA", "id": "90af6fb9fb926dde9f7103577cebc4150bbb1dec", "job_title": "Select-Search%2C-LLC", "place_id": "ChIJq-m4EX3AQIYRJkn4Lhccp2E", "address": "1800 Augusta Dr #240, Houston, TX 77057, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.42318089999999, 29.7345943], "type": "Point"}, "properties": {"photos": [{"width": 750, "height": 437, "html_attributions": ["<a href=\"https://maps.google.com/maps/contrib/106788706324997826205/photos\">Erika</a>"], "photo_reference": "CoQBdwAAABvhcANSwUUJsT77ikHdcvf_VJEC-uV39TqKDwTeE3Pk8ug2jbbBPnT0FNHfr2CfVvLjXkNdcym2-kTcgyJamQZ3ahsd_EAJSr7zCoIhPHomdYVfxA-jN6hkuOVdd-z4qSLtY5P0oVwVAojZd0szKGr7GJFNwWbvd7ktTMAbHpcZEhBrjjorx7bAgFhydysx8ny4GhQQ2nm4krtSBUxjysEUqrpS5a6wJQ"}], "types": ["point_of_interest", "establishment"], "reference": "CmRRAAAA-cJRcHPfpI0KAUoQ4FR2wnk1SnJGZx35-BwUskkTzjeUqnGPV60cPsJ_DdJqkEl8er1zlJciIGOz1Ts1VvJbqTpXK5IoE7EnfgaNuyThAy3-_a9MJTjpNoZNnbmu8REREhCl7RcRTQzK93jaxv3zWrTxGhTFFw84_tpoM7rOdFLtmdeEv6KLTQ", "name": "Student Conservation Association", "rating": "NA", "id": "1c5ea7722fc0d99e9f7dfca55f5d9078224d51d3", "job_title": "Select-Search%2C-LLC", "place_id": "ChIJQcqBXfDAQIYRErawO-goGj4", "address": "2990 Richmond Ave Suite #400, Houston, TX 77098, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-96.038102, 30.055621], "type": "Point"}, "properties": {"photos": [{"width": 984, "height": 985, "html_attributions": ["<a href=\"https://maps.google.com/maps/contrib/110279808588468038448/photos\">Peckerwood Garden Conservation Foundation</a>"], "photo_reference": "CoQBdwAAAKj10OOmSJHZ1rI0O9uy79UL5zM8RPu2Di8yfPAAcIxLphXbdhxOnalhGiavKPXHsGWmErLq6pB_SG80wFIfGVNFpStcTphy4K8hUe5MaTa13q1LstRmIDVwUSaZJ5vdHB7I6USVDtrOm40SN-dln_GEtv0rJqNgCfjgoQefwg0NEhCosjfELYLSZUKrQYs2U9PSGhR0dOtCeGqoFfTj_AP8cObcq2XlOQ"}], "types": ["park", "point_of_interest", "establishment"], "reference": "CmRRAAAA60ua1zRwXQrsiKgWjWhzAkwH4eTVq_oZdgkXuYMTRmPjs3bNIyX-_vqJ5WNlgjsyQY-N0-8UDw4Np0-A3uap90fPRasxpLedRHygTxCmqBOS_fwwFQHqNW25mNRFfVHPEhBuTJz7MZVv9H0ujPisI0OlGhS7w98emN6cW8DL2eaX1og8kuFfDw", "name": "Peckerwood Garden Conservation Foundation", "rating": "NA", "id": "e618a4c618cd67ce4f5fdc165f640220ab3b53b2", "job_title": "Select-Search%2C-LLC", "place_id": "ChIJmUR7pvHKRoYRIIl0o73bPGE", "address": "20559 Fm 359 Rd, Pine Island, TX 77445, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.64386449999999, 29.7515036], "type": "Point"}, "properties": {"photos": [], "types": ["point_of_interest", "establishment"], "reference": "CmRRAAAA3w7Y6GZdOv9NpGgVqVGjuJDzi0JX6TQqSpuLUognvisPLiK5Sb_pFGGMGKXdBoZIsGpQbn_S4AFBPHOjKX_puSGLzPYGvhXykUhbG7VdIL4wJDMQbVcFg27hU_KTtWdvEhBMoLbuQB3rbd9bRJYUymNcGhRWkeeF3s34k6tuUu9i5O5hpUdmmw", "name": "H2O Conservation Technology", "rating": "NA", "id": "30c07988ef8dfc62dac712b9d587daa4a36f2539", "job_title": "Select-Search%2C-LLC", "place_id": "ChIJIWZRKeHKQIYRXxta3wOMGGc", "address": "1725 Hwy 6, Houston, TX 77077, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.5705632, 29.7714443], "type": "Point"}, "properties": {"photos": [{"width": 3024, "height": 4032, "html_attributions": ["<a href=\"https://maps.google.com/maps/contrib/108143329814504597326/photos\">State from Jake farm</a>"], "photo_reference": "CoQBdwAAAAqfxaduLmCpmfn0Z0a9MJQiQD_xGY0vsGW_8Eb9ur9Yk6fVKIqex0Y8ni6cQyeKdQ0G3f8PJ7QDyUUKhnVX59I218CF8ObPLZv16-n5ywKrnKQpx9FAy9ZT_OHoFGFU0f74qov5m2KYV40cplt24LIDJ5UUauD69axRGiQsPuk3EhDwC0J-oRStWxHDSxxvXGU7GhRjUG59XuLYmKNNCzvBAll1vomHFg"}], "types": ["park", "point_of_interest", "establishment"], "reference": "CmRSAAAA9ixV-JnePLhhCa6YTYNn-_2gHwxrt94h2X3gLrrpnSIPY7lIr3CPXGU9--P9X9HxY5BjDYFaQaNoExJewVEBL5vTXzdLqiEMDO6UlgRGojvlq035edhIRMjorXXSzb5MEhAy3SVYXrCCmo45NcC17ToTGhSG68fVTO_pVAn4FnEDczLW11W5NA", "name": "Houston Audubon Society", "rating": 5, "id": "050a5458d86bdd1cee7b09678bd6256d0a20a73e", "job_title": "Select-Search%2C-LLC", "place_id": "ChIJlQOxwVDbQIYR2uX_TZl0TYc", "address": "440 Wilchester Blvd, Houston, TX 77079, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.56820189999999, 29.770778], "type": "Point"}, "properties": {"photos": [{"width": 1800, "height": 1200, "html_attributions": ["<a href=\"https://maps.google.com/maps/contrib/108765250995932379967/photos\">Audubon Docent Guild</a>"], "photo_reference": "CoQBdwAAAHpv-6duAL4mFiEoTQMXDO3LGdpz3eTEao_6tLLoZUB20waiwd8Nxyc8oLDVhF1GNzcjsfIuAGt0XZ3IlNqS-kLz88hA8vVzEaT9E2mOyvpIUlre7N-SRS92x7B5qoSKta8XBij7gS3JFEw6iY9zu4_xmAZMMWTSndJB3LtU-i13EhBMRjEW1DvG0Sxi4GHF_RumGhRb7iCP62eclI_X06lHD6SPqbuHEg"}], "types": ["park", "point_of_interest", "establishment"], "reference": "CmRSAAAANmt7dE21G5EbV298T0P_aVE2u7bH0kZJvU75-5lir9Z3QFc4QZNm4vJqtM8MqaLaRuXe9RXyfnZwRPpzwZPSvjElWnj2cgH-lFPOtqWcAEkoVxJtj0PTXpHk4YeNYWP9EhAKbWJpb1ImmN1Y0hPSUfGSGhQsHbgp1_EPocbCFIzKt3rxqb0piA", "name": "Audubon Docent Guild", "rating": 5, "id": "7ddd5daf76cc4979e2ba6b062322d1c77d5d1c07", "job_title": "Select-Search%2C-LLC", "place_id": "ChIJI9XyNFHbQIYRtwHb8EtTpeU", "address": "440 Wilchester Blvd, Houston, TX 77079, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.44932349999999, 29.7803218], "type": "Point"}, "properties": {"photos": [], "types": ["point_of_interest", "establishment"], "reference": "CmRSAAAAWcZIoUFTVgInudoWqIhd4vIKrV0C8dxxDI5-DanzSsJB_t57p_FgI9Pt4dAKKBC2NDejZ8CbJ13plPwVfEdLZOmRcPYeyyParIA5HHyTuzvKa-1Whl37Qe5Mq5Fwye8IEhADDI1HFclIaLB3E1ap0DsvGhSvgTvIGuPzjxubpp8URv4NMqA83g", "name": "Coastal Conservation Association-Tx", "rating": 3, "id": "7258b034e119f31e82320bca6e72781ee9f79d75", "job_title": "Houston-Methodist", "place_id": "ChIJcekacM_GQIYRPzL13cgQrPk", "address": "6919 Portwest Dr #100, Houston, TX 77024, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.47039, 29.655454], "type": "Point"}, "properties": {"photos": [{"width": 5312, "height": 2988, "html_attributions": ["<a href=\"https://maps.google.com/maps/contrib/101184977609161362375/photos\">aug4</a>"], "photo_reference": "CoQBdwAAADo9KuhqMieZ6uak5yC7Jzz2J9c5UDlubqsvCbY4J4kxM7HG_3_ESj5TrW7hmVnN7MeoVwA4KEWh8Roybvf06QDRBjBP5fB8-9ebIdgdYjJreWceJqO2pFJfyvaPZN-Fm_ByJVTlHMSSK-eVItzxvNH5dv7LRKTTmOFyfrfNdRP3EhBCScOoUWv2wU9i4Z2db7ZbGhRcBxJ0vR9lq9G9d8SeylqNH3C7hA"}], "types": ["park", "point_of_interest", "establishment"], "reference": "CmRRAAAApOayuVYqLGbqZeobhvaJ--jGutBc-1EN0O4Ex2OOKs6eRDs-G5gidBbVzCMgnRAB9sY-FusTpg5BMGa_YHpujmaf02aa4Kll9FeAZ0rlSAEyyUGU3h4aCkqRdYDmgfmhEhDiWmY4dys7VzCVlO9pwgziGhSuztdoM0SO92o0MHu1MgkIZjH8gA", "name": "Willow Waterhole Greenspace", "rating": 4.3, "id": "0127506e8071350c2d48f0ca56e939045297a0f4", "job_title": "Houston-Methodist", "place_id": "ChIJR6_2zTzqQIYRsA7wExgfDWs", "address": "S Willow Dr, Houston, TX 77035, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.4003322, 29.7388505], "type": "Point"}, "properties": {"photos": [{"width": 1136, "height": 640, "html_attributions": ["<a href=\"https://maps.google.com/maps/contrib/117056878997299689379/photos\">Marisol Brown</a>"], "photo_reference": "CoQBdwAAAEAe9F_1lFyQaIVcaDEs62J9JYAjDsv3HrWblERBUGNeWcP6YwTBKeOB_z3rS3mwGe6eMtvrl6GO7Pj-Deimvn4Zb_I6AyKzPY16ozjJS_zAnnhdZwXHWhY7aW_gul_E1DnkwzjR-KeBH_Nd6dTiuv4R42cp3cp_2stJdwttoZjOEhDSuhTlEvD_JEAFyc-I4N4XGhRLXjMYrL1_dwBQasjzEi-yojpy5Q"}], "types": ["point_of_interest", "establishment"], "reference": "CmRRAAAA-UFD3SpULSrrCUbQUUjg3y4p6DYoe46hOWjGRwrNY3pRAwGHlFJGa3lO2HUwDkRg2LHSePFYR2fN4gU23K0BOx9ut9h4f-IlyiOZUUTXWM96uKhogy4hMcfS9B4nNWgdEhCfyE-J_xan8MH5p4Aapn_gGhQjsT7ZcEhnOHosJ3lu2OgvavOkgQ", "name": "Masters Fine Art Conservation", "rating": 5, "id": "a462c2eef4e22ea319485ae7b84f3d20756cbdd1", "job_title": "Houston-Methodist", "place_id": "ChIJp8u2bZvAQIYRbosnWz6cVmY", "address": "1612 W Alabama St, Houston, TX 77006, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.3876169, 29.794149], "type": "Point"}, "properties": {"photos": [], "types": ["art_gallery", "point_of_interest", "establishment"], "reference": "CmRRAAAA7RufLPSZN94hYPb-p3EtvMdBhzoHRRrwS6viOhZ7CUVAW8ndZFvAhwKCtdSDUqAcnG3p37hM8NgDb7Ugf2EejicHAIUHsJxF2CRYcx30vrhWm_8MPmX9WO1USOuY8GpFEhBUoBys4RCkEp51Lh4xmyf6GhQr4iBAWWMoY9yYWkyU10yY02q-nA", "name": "Whitten & Proctor Fine Art Conservation", "rating": "NA", "id": "883a8c5ef35ab28e1630235ad65a6b16506a67fa", "job_title": "Houston-Methodist", "place_id": "ChIJ8YuXE6K4QIYRn1SF1hazFEw", "address": "1236 Studewood St, Houston, TX 77008, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.3858767, 29.7300997], "type": "Point"}, "properties": {"photos": [], "types": ["point_of_interest", "establishment"], "reference": "CmRSAAAArs7MX4xqDsxIhaxqa56v7_nPZhURhIDRyPUMeZ5M5PMGSwjvZoImXDqOX_vDaym0RZi-CvLnFWXN-iNaC7YEWHPAmBnaZWoKuzpGWyf3KGLs93VitLrGpiYgrE2nQhMAEhANj0Du9hEELdbRuyeOICe1GhQwYz_UkPStJeVPUKAub2Rh04hbbQ", "name": "St Mark Fine Arts Conservation", "rating": 5, "id": "ea2d4bac6d74716b33f456dff3aae0cc0b43cca3", "job_title": "Houston-Methodist", "place_id": "ChIJKbDEoXm_QIYRcRFBlp0dE8A", "address": "4901 Main St, Houston, TX 77002, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.483218, 29.7482286], "type": "Point"}, "properties": {"photos": [], "types": ["point_of_interest", "establishment"], "reference": "CmRRAAAA_0ODDt4MPJQbQRZEYJQaE7Eb_s64Ew1MYAsXL9izd5wzEPXWvLqJCKiLJ9vp9hoXujDOf-WTp1_8w6QklGmydf_EFiKg3fg8WJU-6L18stIDjvMVKimpKFHn-IWh7XrNEhA7wOFO6n5KEDZI1gkgUH64GhRY44Z9D653XUw1FvdJEcDFpUuWMg", "name": "The Nature Conservancy", "rating": "NA", "id": "90af6fb9fb926dde9f7103577cebc4150bbb1dec", "job_title": "Houston-Methodist", "place_id": "ChIJq-m4EX3AQIYRJkn4Lhccp2E", "address": "1800 Augusta Dr #240, Houston, TX 77057, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.42318089999999, 29.7345943], "type": "Point"}, "properties": {"photos": [{"width": 750, "height": 437, "html_attributions": ["<a href=\"https://maps.google.com/maps/contrib/106788706324997826205/photos\">Erika</a>"], "photo_reference": "CoQBdwAAAMvtJA_nzKz202zZwe-X089WGWJU-KHzQ6ZODOA6Qa95CcrdUmVrMOo2Nl1O94kRXWNfi1y9dD6IKEjPJIlG9L5QbaphnsJ22IYiIfr6BEY1Mt2NpdOAU3TKuRlq1YsrIqcfePAFfG9Lhyt4Qbhv0qVUTbumo8OAAqGX-AgMIO86EhA0nwhtNUzb6x_r2IR3uWsrGhRjb5RbAfeUKlBOQm_0GD7KPPZ0Zg"}], "types": ["point_of_interest", "establishment"], "reference": "CmRRAAAAdKgMDq6ZDrklf1Z-_6ypVPxajNV_AQrqdHdHlnV4GRUQqKaQR45E6l5OZ2d_IuOkpFS7AdKklf_4DX9EPalQG3AiR4vECZnz4EsWjdV1IfNvViVklRDqa-EpAq1Ihr-wEhCCP63akRIJ6I_SoZBgEIgWGhQFi3DRh6CQWZmXAUV8YueTw4kl7Q", "name": "Student Conservation Association", "rating": "NA", "id": "1c5ea7722fc0d99e9f7dfca55f5d9078224d51d3", "job_title": "Houston-Methodist", "place_id": "ChIJQcqBXfDAQIYRErawO-goGj4", "address": "2990 Richmond Ave Suite #400, Houston, TX 77098, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-96.038102, 30.055621], "type": "Point"}, "properties": {"photos": [{"width": 984, "height": 985, "html_attributions": ["<a href=\"https://maps.google.com/maps/contrib/110279808588468038448/photos\">Peckerwood Garden Conservation Foundation</a>"], "photo_reference": "CoQBdwAAAFKF2dQi38Y1c_9aBOv2SNQJJBjfW0OoQItVoUn25OQejcJO3tIAeMgie_wlv003yEQux5dfwVVdZqW1Gh8o1oOqwLc1GzIT3oqc1vnPpbhdWQnhMFhr5SCJS1piFptyfbuZPret7TIo4HT-sM3CpQbHYISw6diHJWToVFfLXF2lEhCZW_8SQeRbIlLCpqXqLTeyGhT5QkiNiqATdgcZ_o6XNHl9uOuIfQ"}], "types": ["park", "point_of_interest", "establishment"], "reference": "CmRRAAAAccCyd4vfDj7HBo1vkcS4IE-03UkGZrRKHSV1Eq0UfOBLEErDFpKc2vH2DuByfrGP-xwPdjLprE-gnkTxFenQhvYYb1vjFSNTXMJYqFyrg-0iw9y-tHfL2B6qz8lhyaNNEhAu66Fu_2RGcoJbA5WTJH5TGhT1HIEm_jgVaveF0wvprPuJi1MwyA", "name": "Peckerwood Garden Conservation Foundation", "rating": "NA", "id": "e618a4c618cd67ce4f5fdc165f640220ab3b53b2", "job_title": "Houston-Methodist", "place_id": "ChIJmUR7pvHKRoYRIIl0o73bPGE", "address": "20559 Fm 359 Rd, Pine Island, TX 77445, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.64386449999999, 29.7515036], "type": "Point"}, "properties": {"photos": [], "types": ["point_of_interest", "establishment"], "reference": "CmRRAAAA8MLv9oJDEZpImxdRDFJj8XG2pwlCc-3KxPQrTbhZbagRxVUnY6urmKqco8JPM4Cbo1HvN1hSr7g62TTUUihB84kRelfF8yhG7wy3YaqoykIkt5KzX1hI1DeLpTlShT1VEhBisM7goF4_YXn5c6YmrtKXGhTheO6FYKTFkP0k_LZn7g-QtRFdGQ", "name": "H2O Conservation Technology", "rating": "NA", "id": "30c07988ef8dfc62dac712b9d587daa4a36f2539", "job_title": "Houston-Methodist", "place_id": "ChIJIWZRKeHKQIYRXxta3wOMGGc", "address": "1725 Hwy 6, Houston, TX 77077, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.5705632, 29.7714443], "type": "Point"}, "properties": {"photos": [{"width": 3024, "height": 4032, "html_attributions": ["<a href=\"https://maps.google.com/maps/contrib/108143329814504597326/photos\">State from Jake farm</a>"], "photo_reference": "CoQBdwAAAEfRP3do0tHYyEo9fsjPvqiDpQBF6v6eHHVIUzk4REJSGNwVPrUEyYjNbIyRUjoGDTilv_yRkMIN52Mi-fasIJkmrV5hYJOH4QbktcqREFIWLrkUCE9_tJsxknp70_n_FYkOtAVqMSJOrY0_85SdqovX6xN-mGWW87qKqa2bnIIPEhB710d0EDut5G6fqx1-tMCxGhQrlJcfQMX7DEO7bRSLupEWEdFULQ"}], "types": ["park", "point_of_interest", "establishment"], "reference": "CmRSAAAAGTAsR5wdcI2o1RLYA9qu2zDQvdsO6fVIN5SZEK4B-KQ68WTEV3_AxDYNUYt-f08Vf2xJz_gaGGuj5UazhWhF6zr4XhrUTfX3Cl6u3MIT5mLco1uksjR0DWlXcCAFebxkEhCYSo3bI1sqr_01QGdJLMS4GhRH3_ocFSeHTf3Vkv173w_se8YJQw", "name": "Houston Audubon Society", "rating": 5, "id": "050a5458d86bdd1cee7b09678bd6256d0a20a73e", "job_title": "Houston-Methodist", "place_id": "ChIJlQOxwVDbQIYR2uX_TZl0TYc", "address": "440 Wilchester Blvd, Houston, TX 77079, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.56820189999999, 29.770778], "type": "Point"}, "properties": {"photos": [{"width": 1800, "height": 1200, "html_attributions": ["<a href=\"https://maps.google.com/maps/contrib/108765250995932379967/photos\">Audubon Docent Guild</a>"], "photo_reference": "CoQBdwAAAP18gs5kephdDFkqfn5PiYOycqsXlOaFzX1SKozbGMIxLGJwC7ewKDkNUkHePBM0MxvrakAWc7KgSzx2wTHPfptzKcmV3f0bSiMhksOP8Eiuzgz290ZWFzOTKo_jUZmwVmMNP7ur_ZQcFZxEc_FDDmlsOKltMv3IArjIgeJQn1I_EhCU_YJEsXcFsctp90Br7oSRGhQuZBljXNm_2MWkJ2bW5Mr-yXclEA"}], "types": ["park", "point_of_interest", "establishment"], "reference": "CmRSAAAAkFbZ6xlaF7mQ7UUCwFm6pr8f-I8lzh6q6LRnvxlnr4uWxw5b9FBYYFJbvzPjv1Iu9bN9HC3wHXS6bapK2jVh-7qeJPSFOYjkeMQ-GakW6s91LxSs9uvN-HrS6PEwmnSWEhC6DNE24prAK7Cwvsf9lM-4GhShQU8fFd9I81zOJU-vxdnS37jncA", "name": "Audubon Docent Guild", "rating": 5, "id": "7ddd5daf76cc4979e2ba6b062322d1c77d5d1c07", "job_title": "Houston-Methodist", "place_id": "ChIJI9XyNFHbQIYRtwHb8EtTpeU", "address": "440 Wilchester Blvd, Houston, TX 77079, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.44932349999999, 29.7803218], "type": "Point"}, "properties": {"photos": [], "types": ["point_of_interest", "establishment"], "reference": "CmRSAAAAyDP_gsnpNPBYconwQcUXlEdnJ5XDcM5CUCUdiY3yIWx5Q77ROSxAwSBPFd7F5baTjJ9mJ-GIlGLfEEW-Gejln51YlHHhAv7fd7yJNGPjxKI1K_w5bU5vWlf4lWu8_HYhEhC2MBJw8whXvO5ezxLu2yZTGhT8KQwKZUfEQOzClA_PLP277Prwcg", "name": "Coastal Conservation Association-Tx", "rating": 3, "id": "7258b034e119f31e82320bca6e72781ee9f79d75", "job_title": "Water-Utility-Services%2C-Inc", "place_id": "ChIJcekacM_GQIYRPzL13cgQrPk", "address": "6919 Portwest Dr #100, Houston, TX 77024, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.47039, 29.655454], "type": "Point"}, "properties": {"photos": [{"width": 5312, "height": 2988, "html_attributions": ["<a href=\"https://maps.google.com/maps/contrib/101184977609161362375/photos\">aug4</a>"], "photo_reference": "CoQBdwAAAASLMbsvRIwo6iFlZs_xLk5kENqQDYtatadIVVyuOgpP7t-sKmw_6zdNtjni_UwsJU5Nquq5KF7mf19deCqxSb_Ll2-_4pWY6zd71uzz4eBMse3g5XKKLrYoDPzj-WwccmAA38f9wgD7Qo1eagQqkrCx6fMc4kMFEOELwU5FlVurEhChWHNeUE3Z8_mQTUh8Uz2TGhQ6O7DxnoQO82K5Q_6Xyl10OYWJog"}], "types": ["park", "point_of_interest", "establishment"], "reference": "CmRRAAAA7vzewvS4C_fHrtFufL6OGDIfx_fwTSWoDIgGurRILB2z3aufPAGR1t_6a2QISh3dsDah5A14ayEWG_7VQIBv46bCpVQAtfumG0s4q3DwgI-lUzN76tTHJhNkijcOQefpEhDG_u62XzbR07dK6nyCwGZEGhSJtffAId6prqOgTTOIKFGG_auqTA", "name": "Willow Waterhole Greenspace", "rating": 4.3, "id": "0127506e8071350c2d48f0ca56e939045297a0f4", "job_title": "Water-Utility-Services%2C-Inc", "place_id": "ChIJR6_2zTzqQIYRsA7wExgfDWs", "address": "S Willow Dr, Houston, TX 77035, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.4003322, 29.7388505], "type": "Point"}, "properties": {"photos": [{"width": 1136, "height": 640, "html_attributions": ["<a href=\"https://maps.google.com/maps/contrib/117056878997299689379/photos\">Marisol Brown</a>"], "photo_reference": "CoQBdwAAAA_QNmSHr9r0raywO0-jCKGksK22JyHTaYcHP9rKGTFcDp5pnDQVhrsK-BpmdXMoR9svRYm-8kZmCdakOIrR5_GSvXeQC9hGAs6-8KDUTJgMcD2YgHGB1-tVIjwrGTfhk6fzcBX06Dkpjp6ELpTfNagsUuphPDobbZ2tUvFCjE83EhC6R6FB9fxinkZG2o18aaipGhSX6w0v0FCCCZffnG3GG4FljTXS4w"}], "types": ["point_of_interest", "establishment"], "reference": "CmRRAAAA5jbnLKFsdoM-Z070SnYolfTQ8OpttOzQ35mjom2gftaIM6jpw3mzz5vCahCiLg6yWaARXps-IjJkldXyB01NReavWHR0wFU52gOg8Zkc67wHcYe_suH0NCse1cnQrWX-EhAeRxr1UD1FIx9Z3ZrBWS0KGhShxVZ9mczj6ItVgIzwrge4eUefGw", "name": "Masters Fine Art Conservation", "rating": 5, "id": "a462c2eef4e22ea319485ae7b84f3d20756cbdd1", "job_title": "Water-Utility-Services%2C-Inc", "place_id": "ChIJp8u2bZvAQIYRbosnWz6cVmY", "address": "1612 W Alabama St, Houston, TX 77006, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.3876169, 29.794149], "type": "Point"}, "properties": {"photos": [], "types": ["art_gallery", "point_of_interest", "establishment"], "reference": "CmRRAAAA0Spp22vTQHF4kSwJ72IPR-fo1CKfkc8zeiLrla3YdhrtxWsB3lF8bWc-XNoT9u-auxKXMBne1dUAvnYxa6fVA-fkgWNNKCYHXOkTM3iPO8Nv0Umr1DtOpLoyNHwLqtAJEhCn8_eiGd94n7z0bax2bYz2GhSGuorqZkJwxBHArwpludabHq3qkA", "name": "Whitten & Proctor Fine Art Conservation", "rating": "NA", "id": "883a8c5ef35ab28e1630235ad65a6b16506a67fa", "job_title": "Water-Utility-Services%2C-Inc", "place_id": "ChIJ8YuXE6K4QIYRn1SF1hazFEw", "address": "1236 Studewood St, Houston, TX 77008, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.3858767, 29.7300997], "type": "Point"}, "properties": {"photos": [], "types": ["point_of_interest", "establishment"], "reference": "CmRSAAAA0fdNolBPSU6TrQb36jDJh65-3EoinDI3Les_-fX9n8Mq3Yrpzn9dLXppSfOyDS8SEv1X8SWcrNns0n-TsI7YxPr5jJbAM_itJPmBKmdcAQFom3napsHkaWKk2lpOaet5EhBYIiduTWCGBItTUYVXY1goGhScwuVDcYis-ohVq4hzurDZG8tOGw", "name": "St Mark Fine Arts Conservation", "rating": 5, "id": "ea2d4bac6d74716b33f456dff3aae0cc0b43cca3", "job_title": "Water-Utility-Services%2C-Inc", "place_id": "ChIJKbDEoXm_QIYRcRFBlp0dE8A", "address": "4901 Main St, Houston, TX 77002, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.483218, 29.7482286], "type": "Point"}, "properties": {"photos": [], "types": ["point_of_interest", "establishment"], "reference": "CmRRAAAATSZ3fHnNBA785eJ1QL2cgYMUEIIypqIA7ypd-bMxZaEfktDGIrP_sZt7JNXm_dqb6pg5Gk6AUBYgmwuQqGQ2N-gNnsn3HwfNO41jOLjI5sdDrJq1gLyrNt4abB2SvWutEhDorcnORimgBH_BbfJOkqUsGhTWbE3SJ3TnwOwZdETQTYZR7Gj1YQ", "name": "The Nature Conservancy", "rating": "NA", "id": "90af6fb9fb926dde9f7103577cebc4150bbb1dec", "job_title": "Water-Utility-Services%2C-Inc", "place_id": "ChIJq-m4EX3AQIYRJkn4Lhccp2E", "address": "1800 Augusta Dr #240, Houston, TX 77057, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.42318089999999, 29.7345943], "type": "Point"}, "properties": {"photos": [{"width": 750, "height": 437, "html_attributions": ["<a href=\"https://maps.google.com/maps/contrib/106788706324997826205/photos\">Erika</a>"], "photo_reference": "CoQBdwAAAPaHMlrJwiTUNN1Tq-M-pkrobbJ_FWUQV_UokvBFPTJujUAz9XY67JUYMpQNx7c5dNJ7qfYmx-KXtfqOET-l8HEzUU9JQZL1BYhpHFMOH9DUuhRohzhMWlUYVlTh4SBVHJGMxNEoD1pftlNtv1H2OBRgPbvkWZtlfWsT84vkDHzuEhCj8oluBH_NqITLDHdErBAqGhSy3KMl2fxE0Yg7Su-e5YzC9kdLSA"}], "types": ["point_of_interest", "establishment"], "reference": "CmRRAAAAkzlds15WSXZPTWuAcO-3M52E43b3M0C8oolCAB6Aww6cvZXxUc6NlUOzjsm3GjHNQBdVzfIcXVyW-nFdVx8I4H35zR0AktiD_1vdWMX5w46N5vGjIGfjB-GUzohldf0DEhDgA0i69fWz8SK-YNAu7iMEGhQxUwy7gwDMXWeWpX8G-cjV0BWuyg", "name": "Student Conservation Association", "rating": "NA", "id": "1c5ea7722fc0d99e9f7dfca55f5d9078224d51d3", "job_title": "Water-Utility-Services%2C-Inc", "place_id": "ChIJQcqBXfDAQIYRErawO-goGj4", "address": "2990 Richmond Ave Suite #400, Houston, TX 77098, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-96.038102, 30.055621], "type": "Point"}, "properties": {"photos": [{"width": 984, "height": 985, "html_attributions": ["<a href=\"https://maps.google.com/maps/contrib/110279808588468038448/photos\">Peckerwood Garden Conservation Foundation</a>"], "photo_reference": "CoQBdwAAAGbq_aDRPiFQb_4USkzxn_AkJ0gnpKOK0_q2qNo-wNzulAF1sIdS6AHxtBS2ilWRU7ODMmp9IBWWT7ihj8gjfmlR38MvWI7tv2pSLjKX6TaHEFolEjgiJOtTqI80TZzpBYZIH0lxhtlxupkMp97SNA-4PxHsHFc1pPeoAWQD38fXEhDzNyUNY8hHC3DREicLSvOLGhTB2X5G8UrcK5845der3ciu0QQ5pA"}], "types": ["park", "point_of_interest", "establishment"], "reference": "CmRRAAAAsk8bS3YDwlK8WdPTlNr4_VjweXGDzcf5aDq6Ac0Z1QpUFgcVP4UooyCuZZVx1bDb4M-gNkA3raAGuwS1vJoTjj6XESf34IcueEy2bDMutyDBXTeS3tdAKaacPj7lLFh9EhAuMdmu_3Fo4XYVP3v5LLRWGhR5wdCXIt3PLEFo16KQuVnWs9g0FQ", "name": "Peckerwood Garden Conservation Foundation", "rating": "NA", "id": "e618a4c618cd67ce4f5fdc165f640220ab3b53b2", "job_title": "Water-Utility-Services%2C-Inc", "place_id": "ChIJmUR7pvHKRoYRIIl0o73bPGE", "address": "20559 Fm 359 Rd, Pine Island, TX 77445, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.64386449999999, 29.7515036], "type": "Point"}, "properties": {"photos": [], "types": ["point_of_interest", "establishment"], "reference": "CmRRAAAA9PPPkIV-__qynOQ-zIvl7CZrX7qH5SoFCMWlhUqV5j2tEzb5QL0vbO5X8SNq4nvaizrH5CNEhxBdOWJHi584kcy4JorofHsPx3equw2znc4Y_BdP7mwnsxQEQjYxvvwVEhBPqRQzpSzu1UVKqVRz43vyGhSAFiJ8xXQXN6ftoE9DDdIhyb92Ig", "name": "H2O Conservation Technology", "rating": "NA", "id": "30c07988ef8dfc62dac712b9d587daa4a36f2539", "job_title": "Water-Utility-Services%2C-Inc", "place_id": "ChIJIWZRKeHKQIYRXxta3wOMGGc", "address": "1725 Hwy 6, Houston, TX 77077, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.5705632, 29.7714443], "type": "Point"}, "properties": {"photos": [{"width": 3024, "height": 4032, "html_attributions": ["<a href=\"https://maps.google.com/maps/contrib/108143329814504597326/photos\">State from Jake farm</a>"], "photo_reference": "CoQBdwAAAIZqC1CR4fHHgwWsZHQRGqFfbghKB3F5r8Lt3qC8FEw540DLivcCuxsDswtZ3GVUiubjaYeP_ojjo73EVxXIhd9PTZUfRRxhtqARETETUZdVb2yoyG4rDns7EvlzwPxk42J7jSNJ8VrUAQ5CCvPS7F0rup0awX3jz2dlsC2XWyYREhCgQVFcI3PbxrsC_FnsapRiGhTRVryqBEQikQWTMxnr4DYdJpIYtQ"}], "types": ["park", "point_of_interest", "establishment"], "reference": "CmRSAAAAz-znuW3Cljg5rQkvE2CW6fLsD84RJyBMoDSzOj0-tTofy1CtyJ8q0ldd6ZHfOzgurDna2WJ4Q3sDNafh8s0XtNTbkXjT1ed5DgtYj8i5UTatsrSx7m25uz7oztX_7kbJEhAbbImE2Mtk3NWxeW2p6Q00GhSISn294JTiln5zq_Cdo62_FXf35w", "name": "Houston Audubon Society", "rating": 5, "id": "050a5458d86bdd1cee7b09678bd6256d0a20a73e", "job_title": "Water-Utility-Services%2C-Inc", "place_id": "ChIJlQOxwVDbQIYR2uX_TZl0TYc", "address": "440 Wilchester Blvd, Houston, TX 77079, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.56820189999999, 29.770778], "type": "Point"}, "properties": {"photos": [{"width": 1800, "height": 1200, "html_attributions": ["<a href=\"https://maps.google.com/maps/contrib/108765250995932379967/photos\">Audubon Docent Guild</a>"], "photo_reference": "CoQBdwAAADkVKlWL7zRrTOtNjqY6gYAJOJN5R-fSQ6T6vIqA1z0pdLhIr-DIFGqhWgaKRdrcy-Bc4KYPLuBai0Sie5x152-IDZgyL5qOnsSWUjHslKwe0oWalU7wxulyxQtr1YmLjRtbhLT92MGHvq9Vyj5a6gB7LEqNfwZjD-SdDnWg2PD_EhBLxtI8Xs7KC_8xMc5P2lS1GhQNnVP3wUHuFRc4kNU6SlYfztJIQw"}], "types": ["park", "point_of_interest", "establishment"], "reference": "CmRSAAAAtKgKZEcJGM3B_i3o1G2MhK0b3sZrLiO0UAlB_hiAxQnkyiliFBk-l3B19TZOIzBvCa2fX-aRQF89mP1iI9Ax2wzmlwQOUEbbqaXTTDz_MjDoFmOegPmQ_uiYhQxspuqNEhB8jYfVaah0ux_xQfbhPBKRGhSmT6RBpYqechNFTwVOtxWnd94Hbg", "name": "Audubon Docent Guild", "rating": 5, "id": "7ddd5daf76cc4979e2ba6b062322d1c77d5d1c07", "job_title": "Water-Utility-Services%2C-Inc", "place_id": "ChIJI9XyNFHbQIYRtwHb8EtTpeU", "address": "440 Wilchester Blvd, Houston, TX 77079, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.44932349999999, 29.7803218], "type": "Point"}, "properties": {"photos": [], "types": ["point_of_interest", "establishment"], "reference": "CmRSAAAAduZrJmSG4_0f7kDyDi00ods25lY6MyKW0h6o5ssI7hLveDiN1-xAZzzy_RTX4hdKrAh_bcC0QnKjX0fLHpUfCEa0lhiEnYFpYwaxPaSKnXuNSHIEjzp_StuHImmr4dIDEhA47X7JTBInxZ3nMZjlS7lEGhR0jMHMbY3kJnMW9KmL7F8SAVCOUg", "name": "Coastal Conservation Association-Tx", "rating": 3, "id": "7258b034e119f31e82320bca6e72781ee9f79d75", "job_title": "Joco", "place_id": "ChIJcekacM_GQIYRPzL13cgQrPk", "address": "6919 Portwest Dr #100, Houston, TX 77024, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.47039, 29.655454], "type": "Point"}, "properties": {"photos": [{"width": 5312, "height": 2988, "html_attributions": ["<a href=\"https://maps.google.com/maps/contrib/101184977609161362375/photos\">aug4</a>"], "photo_reference": "CoQBdwAAAK0LO0K1_tRFDXi0jfCD2YXNZznzHtbIHGgEwWTglvLa4aPEKmq1x2ApwBkvUZKYMlb5ZazJ0Upu6IkJyiEvm8_4PTjTSFAa--5Lj3weHU2FNjM3w3kMU0ho7kOhox_3LuPdQ_-oIovBsmAtsN_RD7yI4EKPmlNxtRjt7zvlsA-sEhD2-Ar0zhMGNQRFAb90HHl-GhTkRkbPOKQbofo9W7AvSEoIUy-h6g"}], "types": ["park", "point_of_interest", "establishment"], "reference": "CmRRAAAA_7kFM4_2L8U_wFirpIdcuwbmTyJAEj9PTUcTf5khlJgRH24ERrf-j1aUUdNrVmg3BYd03jgWO4a2ExUxRjh6ukAQ3IHhIa3GU6qUbE9pS5W6OnbOq1Qlne99EFt1w3voEhCbxXd9mhp_yr-TAoDGnsm4GhRgRe9QgB-27LvP7cdiBLVgLSl-ig", "name": "Willow Waterhole Greenspace", "rating": 4.3, "id": "0127506e8071350c2d48f0ca56e939045297a0f4", "job_title": "Joco", "place_id": "ChIJR6_2zTzqQIYRsA7wExgfDWs", "address": "S Willow Dr, Houston, TX 77035, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.4003322, 29.7388505], "type": "Point"}, "properties": {"photos": [{"width": 1136, "height": 640, "html_attributions": ["<a href=\"https://maps.google.com/maps/contrib/117056878997299689379/photos\">Marisol Brown</a>"], "photo_reference": "CoQBdwAAAFE4Xk7j1vtvNl6WgzIIfzzoM7oHkX-_Ggsarw7yPjNtWIN2kEHrEMqKZXHOqWzd49jQ51fc4Vh1in53SRP5_4EH5K1VFJju4ytriFwVnxhNpnjiAymek0Axhv4-OUjIwLPEMjeYDKe4JMcG27tgBu4YciAZPM6fDVJrQjluLlJtEhAnBaHtp-36iGPOAkYUidToGhSQvcDKbVICinvPlySKRPpQPIFi_Q"}], "types": ["point_of_interest", "establishment"], "reference": "CmRRAAAAMbkR9ZaKw9qRvrQmDnSR1d7D7RRQbUJtHICaJBy8roO7oaUv9GhgdOu_t96jP15UFT5N2cHhumbT9Iv2lRtdqBNYS573Zmuoos0pRxMBf-BtJ58sWFX4ANsjQfdVKmveEhCHIkcQI5xf6CSMcPBE2hmoGhSD16vSA6UtcaDzP-IFOXg3msI9Lw", "name": "Masters Fine Art Conservation", "rating": 5, "id": "a462c2eef4e22ea319485ae7b84f3d20756cbdd1", "job_title": "Joco", "place_id": "ChIJp8u2bZvAQIYRbosnWz6cVmY", "address": "1612 W Alabama St, Houston, TX 77006, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.3876169, 29.794149], "type": "Point"}, "properties": {"photos": [], "types": ["art_gallery", "point_of_interest", "establishment"], "reference": "CmRRAAAA8LiAUJdJ-l_Vkl0SnuABeC8HpS5ujEaAP8DPHt4jfpjxu1QxozLBhfsL2tPbdf_lmS0PmgZV4kf6I7xaFmnqiB75p44LP26bDXxh8a0osvpZoRfDtvua_SjAnX_s1N9XEhAUhIgbMVkeEyr-A6H5ZDGBGhSwvckpe8hSJm11N1rShtvIJywVQg", "name": "Whitten & Proctor Fine Art Conservation", "rating": "NA", "id": "883a8c5ef35ab28e1630235ad65a6b16506a67fa", "job_title": "Joco", "place_id": "ChIJ8YuXE6K4QIYRn1SF1hazFEw", "address": "1236 Studewood St, Houston, TX 77008, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.3858767, 29.7300997], "type": "Point"}, "properties": {"photos": [], "types": ["point_of_interest", "establishment"], "reference": "CmRSAAAAk6ZlVSlWgYoC0r9LZIYpIut5EOa7TTxb8b5ihP_ATFoGBNJlT2UTw08WSteOywXtn_2QMf5raSMKD1rSap8gXVBuDZEMWoAt7uCcTK8d1uSVNB6WNWNH16IwJ4fbE0kkEhAEW7_-lBSdcp0xiYCvfJndGhQwqArIFhxu0IV51Me3ZzTPwSX-4A", "name": "St Mark Fine Arts Conservation", "rating": 5, "id": "ea2d4bac6d74716b33f456dff3aae0cc0b43cca3", "job_title": "Joco", "place_id": "ChIJKbDEoXm_QIYRcRFBlp0dE8A", "address": "4901 Main St, Houston, TX 77002, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.483218, 29.7482286], "type": "Point"}, "properties": {"photos": [], "types": ["point_of_interest", "establishment"], "reference": "CmRRAAAAlcTY_ywYNJ-TgaxkApqh1rTVxptENGm8Nt0Uf3Ui3JuuhU5juOX-aemjblZMMEDo15IiWoQpRPeF9hM8F82YLz311O6-yB5LdN29edk0-O8QSzzNloweMXdSsHodcrgMEhCkGDKCIvX4N5lqLVKoid0_GhRDir9yVhAKUIQY8o-_sXmKfvxXog", "name": "The Nature Conservancy", "rating": "NA", "id": "90af6fb9fb926dde9f7103577cebc4150bbb1dec", "job_title": "Joco", "place_id": "ChIJq-m4EX3AQIYRJkn4Lhccp2E", "address": "1800 Augusta Dr #240, Houston, TX 77057, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.42318089999999, 29.7345943], "type": "Point"}, "properties": {"photos": [{"width": 750, "height": 437, "html_attributions": ["<a href=\"https://maps.google.com/maps/contrib/106788706324997826205/photos\">Erika</a>"], "photo_reference": "CoQBdwAAAGsi8SvHnrB6CEU_4ty1cQJyWffQ5aPGj7LKah611notT3ZnGSVKl2uXTdWz6maKms53bLWJytdgtcl0Sh9XZ6Pc-p4iLsYsDfZKdXPFAl4ARxYKq5tA_LHag0s0XyJnNgILeWTmaMoirxb1p2575r_6hUTWySdez747AMLXLIeCEhDc_1OgtrwOlgdiW9DcOg0KGhTEz0ZpOpia5L8BmWz9sbpAtjPgwQ"}], "types": ["point_of_interest", "establishment"], "reference": "CmRRAAAAvnC6DSW2cg86hiM_NaH71ZsLHGPkLjSMTi1gLNN6HFZN-RJLXFPHY-HLaG5oipUaGs6yR7gd8fU0QEMkfZTnZ7xwij4XuzxZryQeSKlbP-JPAxdIqrm9-5Kerec4ofDeEhBdw63n_y_zzHfH0sAnKU4OGhQ_RPORZtl50PywPF0-9vE1Uq7dZg", "name": "Student Conservation Association", "rating": "NA", "id": "1c5ea7722fc0d99e9f7dfca55f5d9078224d51d3", "job_title": "Joco", "place_id": "ChIJQcqBXfDAQIYRErawO-goGj4", "address": "2990 Richmond Ave Suite #400, Houston, TX 77098, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-96.038102, 30.055621], "type": "Point"}, "properties": {"photos": [{"width": 984, "height": 985, "html_attributions": ["<a href=\"https://maps.google.com/maps/contrib/110279808588468038448/photos\">Peckerwood Garden Conservation Foundation</a>"], "photo_reference": "CoQBdwAAABGEXLPWVJcO7_5FQae6JHokwwgJ72XRQpNwNlJWFbqi1yFu47hFiirxRBpqXTu0MzJsJSJRAZ8vMuPtKt8Qjp3oEZSe-MeMhAgVldrf5smB_Dd4TDRCFHLDnkXiL_GL0sRehjgbND4WbBh_Rj_WUJA1Ptn_22fxBCFZr_FodcAtEhAQai7ekdonx4Y8YJsvqc-bGhRtR4ubD4y200GtfCTkDlWUmPdyjw"}], "types": ["park", "point_of_interest", "establishment"], "reference": "CmRRAAAA4RYu_7S2LvBNjclv3FdLYFRhzSLN8avnprn_u4ny0aki5_1ph2A1FsnL5sui1BbsANYY7Cq9HhDPluQWH4CcBst6QVGgT46PBCR8SnX7-a2haP0Xd7wu28zowKkvZBp_EhC9pyFc_jCrbAoEFnv_Q4R3GhRhf-UBxowOeAGYu28IsVdlYu-3bg", "name": "Peckerwood Garden Conservation Foundation", "rating": "NA", "id": "e618a4c618cd67ce4f5fdc165f640220ab3b53b2", "job_title": "Joco", "place_id": "ChIJmUR7pvHKRoYRIIl0o73bPGE", "address": "20559 Fm 359 Rd, Pine Island, TX 77445, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.64386449999999, 29.7515036], "type": "Point"}, "properties": {"photos": [], "types": ["point_of_interest", "establishment"], "reference": "CmRRAAAA56GDIlrK-OXSSBGubiBlptvmqLpY319EhHbxglpf2F3YcGLu8ugrJ2WwLg1Iflvbuh8xcIEBpZYJUbhRLlMgEdkMwEgJ2zGoKJqRVOkU4GZ77zDGdUgt_FJj1huV-WInEhBlTdMRJ__aHuZbi7Tc2E5BGhQ1vZQONzbKFAS9vr62P7GwI0Xptw", "name": "H2O Conservation Technology", "rating": "NA", "id": "30c07988ef8dfc62dac712b9d587daa4a36f2539", "job_title": "Joco", "place_id": "ChIJIWZRKeHKQIYRXxta3wOMGGc", "address": "1725 Hwy 6, Houston, TX 77077, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.5705632, 29.7714443], "type": "Point"}, "properties": {"photos": [{"width": 3024, "height": 4032, "html_attributions": ["<a href=\"https://maps.google.com/maps/contrib/108143329814504597326/photos\">State from Jake farm</a>"], "photo_reference": "CoQBdwAAANYietZUtfyeaRVnWw-6URzzHk086spv2o1RWjNDHExTABpRuH827KA4_24Sphwgq9wUJoGCAxRxWjdUh4Q547vwzArf2BsMDvdn7AJiBdqKgWaOC2ZaBn_47GY499JcpXCPRoOC6q2DuU3pTFIgZRcqhwDWLJZu6KkSFN7lOl3HEhB1hX22MriIwAr--eJOOb7SGhRV_kZqOxPcuGpwFvlJXwUrabu05Q"}], "types": ["park", "point_of_interest", "establishment"], "reference": "CmRSAAAAedltIc_GyLO-72ZrCeo7_zWYiituF_Zq7bY0ud_pSXY1hKfEGlm56Qz4bvm2mHz0-l8IMhg8UHEKxpxUTLNSU8G19FoHrNfPiKh6n1U00Hab5y_-9WLr2jb6L-nSrSm5EhC8EyIhyDFABPNm-6hGmun4GhTvnL3dinbrxxq-a8Jkn8q_fv-8LQ", "name": "Houston Audubon Society", "rating": 5, "id": "050a5458d86bdd1cee7b09678bd6256d0a20a73e", "job_title": "Joco", "place_id": "ChIJlQOxwVDbQIYR2uX_TZl0TYc", "address": "440 Wilchester Blvd, Houston, TX 77079, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.56820189999999, 29.770778], "type": "Point"}, "properties": {"photos": [{"width": 1800, "height": 1200, "html_attributions": ["<a href=\"https://maps.google.com/maps/contrib/108765250995932379967/photos\">Audubon Docent Guild</a>"], "photo_reference": "CoQBdwAAADPpM0GQJz7ElQ4nhYM7Cn2koAgHy28aplXgf-bKsZqWhIYnAtAhE2jtlQq8INHj9ZjbKuzZQxtBZ5CULD2s1co8Z140mwX4XDrCCtrERvnl2Ej4LgEbySkgegM2PDQXnaOfdhTmmqjB-0UdxY8OACI9gtZm-Pu7TvbtBhxZl6hbEhA7oBpkV51ksnLW1U9FCZZCGhRDJ9fbgXqUVt4zKVflo2vZiWgESQ"}], "types": ["park", "point_of_interest", "establishment"], "reference": "CmRSAAAALWijpWPH4MD-atJC_H9VcyCXYSEc2TlnLXVx_b58nkdYkQaJ5BJVx7eV4kAzXS_88otE1pJmTM9kALn4WPc3PrOSvpC6rPX87J6FRWsQRi4qIjWIR4WMbFekkKd-Uh7eEhArBHA7A_gH66ZXCKh3k1YVGhSykbgcpWnPzFDSiamtn_p-Jkotww", "name": "Audubon Docent Guild", "rating": 5, "id": "7ddd5daf76cc4979e2ba6b062322d1c77d5d1c07", "job_title": "Joco", "place_id": "ChIJI9XyNFHbQIYRtwHb8EtTpeU", "address": "440 Wilchester Blvd, Houston, TX 77079, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.44932349999999, 29.7803218], "type": "Point"}, "properties": {"photos": [], "types": ["point_of_interest", "establishment"], "reference": "CmRSAAAAUDvvwK7pKyUYu1SprCJVTAiLwWmNiaV0IGmPY5BImPmYMmNOnJywxLOBJIMLlWaSEozPgpBurHvlU1ebayglsE0JjYI406AzDvhPOjdSeZ1Bs9783oq16-c8xOTlJjsuEhAFwSMdpDurppsBaLvITH-uGhSJc8Ce2zskOkMU0KSrYR_vibseIA", "name": "Coastal Conservation Association-Tx", "rating": 3, "id": "7258b034e119f31e82320bca6e72781ee9f79d75", "job_title": "Lja-Engineering,-Inc.", "place_id": "ChIJcekacM_GQIYRPzL13cgQrPk", "address": "6919 Portwest Dr #100, Houston, TX 77024, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.47039, 29.655454], "type": "Point"}, "properties": {"photos": [{"width": 5312, "height": 2988, "html_attributions": ["<a href=\"https://maps.google.com/maps/contrib/101184977609161362375/photos\">aug4</a>"], "photo_reference": "CoQBdwAAAFNhgVoG6CeH0n9xEp7mNdAKOA1vRSO4jHgnaeBZi8siZTToD5NXiEktVcQojUsVPG5ih_9AkdEBHXg1gTI2tloureKxCI5NFi74VrvSt07uP0RklQ1FzAYy4sAMqipHjidvxiIxqRrujGDmrkkmi3q7ZlomLIgqP1mEI6xPXrPDEhCCF-vhP00RrDYEjcNVf3hMGhT5EZ2ptZSXIBS6EOElBMM0KW_Wuw"}], "types": ["park", "point_of_interest", "establishment"], "reference": "CmRRAAAAAZxQimcWYdIu54Y0klTg8A0Gn8NPJ48Px8nkPB2wV4m5fDGVEbecGKM1MLPH2Edxyko0MEG3Yt6FyIBD3QYHLsQkADi9f-zNj7BOyJeImWZQVp7NnIqRWFrNvwlESm9ZEhCoy-sQZOd6y6RlqY3iPenjGhS1N-9A-lgrYSIzDutLKrFKynE98g", "name": "Willow Waterhole Greenspace", "rating": 4.3, "id": "0127506e8071350c2d48f0ca56e939045297a0f4", "job_title": "Lja-Engineering,-Inc.", "place_id": "ChIJR6_2zTzqQIYRsA7wExgfDWs", "address": "S Willow Dr, Houston, TX 77035, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.4003322, 29.7388505], "type": "Point"}, "properties": {"photos": [{"width": 1136, "height": 640, "html_attributions": ["<a href=\"https://maps.google.com/maps/contrib/117056878997299689379/photos\">Marisol Brown</a>"], "photo_reference": "CoQBdwAAAJ5q20QRIZsvp84eoyeouYMOmopmsuxXhIL--osg7d6QAjG9Jqft4HJ_SbsgYNKgXDXqbS0BnfHfdDkepJ0ZeUR84QF3EtDumrw9y8hWJv03E1xRO19I3qWgKBAbYERN7dlj92AY0ukElKkeAttC3IOP0VO139vaM7vGaSVj2WYSEhDhO2NWf9V8NtQIBgm_Iop-GhQOeL8ftk4M6FphfQzdmmL8nMa1xg"}], "types": ["point_of_interest", "establishment"], "reference": "CmRRAAAAc-u9qnl4iy_9avWpQ-N9Q07bJX0vdM4xufiiawc5qQvuJOW7-vtwyec5RJAdYqwaxE9N1kGIx16kZaVHrVEsNyqXoJxI1UwDjvvvE8wz5heNGq7kuC1MZvXOKi3ZTQs8EhCtW70gCwQR2qpIOVHeNxvgGhT7WQUlvs_aQ2_bdk3iiJMDJ-Uxsw", "name": "Masters Fine Art Conservation", "rating": 5, "id": "a462c2eef4e22ea319485ae7b84f3d20756cbdd1", "job_title": "Lja-Engineering,-Inc.", "place_id": "ChIJp8u2bZvAQIYRbosnWz6cVmY", "address": "1612 W Alabama St, Houston, TX 77006, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.3876169, 29.794149], "type": "Point"}, "properties": {"photos": [], "types": ["art_gallery", "point_of_interest", "establishment"], "reference": "CmRRAAAAJTa7NBPf3Ejl1YSD_QlwDi1gA6sANV0JswAN4HeHypOp-XZxEYDDEUk80wg_hxWLip6SWwxA106g6jF9i9_YpXfhUCGJvXa4ZEQ3Hi_THdwSQVOalxC0Qeom9H-zxfm3EhAkATzCf2RusoA5dbwtCdu_GhTco-GtQrRNMDwaSX8TkWzun3mw7g", "name": "Whitten & Proctor Fine Art Conservation", "rating": "NA", "id": "883a8c5ef35ab28e1630235ad65a6b16506a67fa", "job_title": "Lja-Engineering,-Inc.", "place_id": "ChIJ8YuXE6K4QIYRn1SF1hazFEw", "address": "1236 Studewood St, Houston, TX 77008, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.3858767, 29.7300997], "type": "Point"}, "properties": {"photos": [], "types": ["point_of_interest", "establishment"], "reference": "CmRSAAAAOr1vRYjqRc6nR5RWh9fr0bdt_QGuOQf3OuA93hS8vvPdPQinLdiZ0JjMaN9HgOwa0tdPU86pgPm793AmgiMnH6ZWJrbX7tEpChRFmIFEvbAMNCg8feuXtTl5IBk8daYFEhDAN9uX-c0yMg6A5PoG7UuPGhRV19HA5353dQlElq-MpipCuFDryA", "name": "St Mark Fine Arts Conservation", "rating": 5, "id": "ea2d4bac6d74716b33f456dff3aae0cc0b43cca3", "job_title": "Lja-Engineering,-Inc.", "place_id": "ChIJKbDEoXm_QIYRcRFBlp0dE8A", "address": "4901 Main St, Houston, TX 77002, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.483218, 29.7482286], "type": "Point"}, "properties": {"photos": [], "types": ["point_of_interest", "establishment"], "reference": "CmRRAAAAKq8BAsMnsphb1X9i2HbNof2lF0qz6UEAh1jSFgEJDO3zY0z-pZFkaEdmwA5LiOd9RXfO_X1Z2xk91Xey3Tpl8ko2iti0JBWJ254D0IB7rHVart4MgmLpVcLcWYsEUzdwEhBMdBjYW_dwL2rurqa3mSvrGhSBh3qNoO4_qQJWXa47e46-JJSbHA", "name": "The Nature Conservancy", "rating": "NA", "id": "90af6fb9fb926dde9f7103577cebc4150bbb1dec", "job_title": "Lja-Engineering,-Inc.", "place_id": "ChIJq-m4EX3AQIYRJkn4Lhccp2E", "address": "1800 Augusta Dr #240, Houston, TX 77057, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.42318089999999, 29.7345943], "type": "Point"}, "properties": {"photos": [{"width": 750, "height": 437, "html_attributions": ["<a href=\"https://maps.google.com/maps/contrib/106788706324997826205/photos\">Erika</a>"], "photo_reference": "CoQBdwAAAP6M3ELYv2rzeZ01s9RXIZOVaOkF6YL2Q0YbO-FEROa3adSVstPByzpbHwhUUHJgyoBR3W5gO2S1MAiG0UM6r_iI9icwXi5sMbLl15LtXipcucaVQI1zMNoJEUHDg3V-qE4nsMo2NKUIJljZP9tdQFWdEgt2oyhn73rS7HNU1T3tEhChXtNqrh-HOsZXTTfku-nNGhQ5K7294O_wFOrKBhNIOwKkucmrww"}], "types": ["point_of_interest", "establishment"], "reference": "CmRRAAAALy03v1KiaLT6JQMmwVcjt2DX-mA4hO-xuVpDkkPxSOMWEUJBn_9vuXUrHdAtmI7-o_qgryXe_r8e16pmzJlf374NkMB0rY4pxhM55JLZPQgPmbSzdvv2-tPnINQQnIjcEhDTE2wCwz7ZBK_H_RenoU7TGhS5mNlMM1WONGWTOz_cBL_GJU45GQ", "name": "Student Conservation Association", "rating": "NA", "id": "1c5ea7722fc0d99e9f7dfca55f5d9078224d51d3", "job_title": "Lja-Engineering,-Inc.", "place_id": "ChIJQcqBXfDAQIYRErawO-goGj4", "address": "2990 Richmond Ave Suite #400, Houston, TX 77098, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-96.038102, 30.055621], "type": "Point"}, "properties": {"photos": [{"width": 984, "height": 985, "html_attributions": ["<a href=\"https://maps.google.com/maps/contrib/110279808588468038448/photos\">Peckerwood Garden Conservation Foundation</a>"], "photo_reference": "CoQBdwAAAEDjgmq_aF38-xWngCXLWS2v4zLdR4LXmwP7wQjtwUUXRxVClu-pnc8rUw8ukdabtZQHmXH_3XrzaZmIkeZSXclRC7HQfsX6F6R7syaesqJKC6DhMYFBBu-7Ik_f039VPib7UCUr8UP7S4NSPJRgRqRoMPVZiYgDD3BpzZ-CnCuoEhAlB8xXJVBjLFiLzYHplLmEGhQjXNQ1deD185Y5A0i42xpV-qkbNQ"}], "types": ["park", "point_of_interest", "establishment"], "reference": "CmRRAAAAVY59JcDwTSag4cDHoIK4Lg0Qie7M3JYDt1mvk9Y2KZ2YUPXum7WeBBnhl1zCNZ4EoOeEXVl1PbhDtm3exd2-pd2FAkuNypDMzwm0YQ3J8-nh2159VangBQSysGCE4_gyEhCElTKVgQ38I8lvK65jOjX0GhS8swVn_DYK39ZPAQqBWf5OvvByTw", "name": "Peckerwood Garden Conservation Foundation", "rating": "NA", "id": "e618a4c618cd67ce4f5fdc165f640220ab3b53b2", "job_title": "Lja-Engineering,-Inc.", "place_id": "ChIJmUR7pvHKRoYRIIl0o73bPGE", "address": "20559 Fm 359 Rd, Pine Island, TX 77445, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.64386449999999, 29.7515036], "type": "Point"}, "properties": {"photos": [], "types": ["point_of_interest", "establishment"], "reference": "CmRRAAAAY7r0L6nY0a4DQxTeoC3NaIRU8vyz3AfaH4fsXd3v0Sz2IT2Su0sSYf-pkmupxwDZz-dxl3pYD9abbQxAyXd8BZomPZX6qRRA8evm38zzdP--6vJFcKsu6sFJRfzW7MbXEhAB5P5U04xtxrl2d_M_yFADGhST6GspyaaawX7sMrR61rAvEcxvXg", "name": "H2O Conservation Technology", "rating": "NA", "id": "30c07988ef8dfc62dac712b9d587daa4a36f2539", "job_title": "Lja-Engineering,-Inc.", "place_id": "ChIJIWZRKeHKQIYRXxta3wOMGGc", "address": "1725 Hwy 6, Houston, TX 77077, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.5705632, 29.7714443], "type": "Point"}, "properties": {"photos": [{"width": 3024, "height": 4032, "html_attributions": ["<a href=\"https://maps.google.com/maps/contrib/108143329814504597326/photos\">State from Jake farm</a>"], "photo_reference": "CoQBdwAAADq5Qj7BA96PIKxacLG1_8dXTX45RWWJaE4tKVPc2MuM0oS6TRmSLp2M8DDvR6rxWT8Rg6pyteZDs0_hmLLpM8StyG9dZzswNC_t4P9h3zHGVp5qjbh7arqvxvH6cqJ5docvxT45nl1Aima-UVMejl-WDvESJmjf7_bpX14ZX2xQEhBnB_RjTv8ps3D32ZLIQwoCGhRtbPCstcWAYpfIi7LzXRmEx4JCAg"}], "types": ["park", "point_of_interest", "establishment"], "reference": "CmRSAAAAmwFyfLhh4ug2D85O8KgvdBAfg1YBuR5ZLUSOyDh5IgC5jK5BdPcZKTQNEToJyK7gtduYNGqczPG8T8RHqmLt0ONsUShhico72OSfoCoHf7NFOkKFg_Jna-lES1Mxk9DHEhCSiq5dTG0fSnRIKTMsw96rGhSElqnVAbnQ-d0yePedzs-e9-VDTA", "name": "Houston Audubon Society", "rating": 5, "id": "050a5458d86bdd1cee7b09678bd6256d0a20a73e", "job_title": "Lja-Engineering,-Inc.", "place_id": "ChIJlQOxwVDbQIYR2uX_TZl0TYc", "address": "440 Wilchester Blvd, Houston, TX 77079, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.56820189999999, 29.770778], "type": "Point"}, "properties": {"photos": [{"width": 1800, "height": 1200, "html_attributions": ["<a href=\"https://maps.google.com/maps/contrib/108765250995932379967/photos\">Audubon Docent Guild</a>"], "photo_reference": "CoQBdwAAAHjRZrjvSYpOB36blQmjwbsblbtywy9_fWCh06VjQc4HY-KS4rnSIPe0M6qAVRph9wINA8mrqQTaBEgP79BXggCJgkqKe_EV2qpieR2tgDqmnwlIaKPBGTVbyXBGeKQyNMx96OVb-LsFh5pgURPM-q1M28yJYPqT8p3RT2InXIPYEhC1wLMzbm1FNoCeAhNE2OQ5GhRece-96SCN1ny2wVhrd9bbpsc4Kg"}], "types": ["park", "point_of_interest", "establishment"], "reference": "CmRSAAAAiZ1f3-etdDBpJcWH37cNf2XTjAvUgYKj6qxniiJy3bpU_n0DnzBC9alzqOdVH_l5OCUwUI7lvOWOMBebx-8u44G-_RyTPm4m3JUbdK09YRs2mgrQx_t0r4K3PiT8zY7UEhCsHce4pyXDshEWxqsXLhbkGhS3MpeUUcvZuQCcuOnazvEpdjjBEw", "name": "Audubon Docent Guild", "rating": 5, "id": "7ddd5daf76cc4979e2ba6b062322d1c77d5d1c07", "job_title": "Lja-Engineering,-Inc.", "place_id": "ChIJI9XyNFHbQIYRtwHb8EtTpeU", "address": "440 Wilchester Blvd, Houston, TX 77079, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.44932349999999, 29.7803218], "type": "Point"}, "properties": {"photos": [], "types": ["point_of_interest", "establishment"], "reference": "CmRSAAAAd4biWhwnr7mia-OA6xvhjwQsbPM6PtMEb-8KzHtZWHeU9X21I6OctSCA8pcoKc_ep6rwq3EOWI649u8Ruu_qzyn7kK_d8kwgA_1iC07RNoNHZ1-X3Rrb8jLH36BklWtbEhCfslEZlm-JniBrGkROOE7pGhQ-ooj-jrTQYcHdGasxdSTUmHtNVg", "name": "Coastal Conservation Association-Tx", "rating": 3, "id": "7258b034e119f31e82320bca6e72781ee9f79d75", "job_title": "Surveying-%26-Mapping%2C-LLC-%28sam%29", "place_id": "ChIJcekacM_GQIYRPzL13cgQrPk", "address": "6919 Portwest Dr #100, Houston, TX 77024, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.47039, 29.655454], "type": "Point"}, "properties": {"photos": [{"width": 5312, "height": 2988, "html_attributions": ["<a href=\"https://maps.google.com/maps/contrib/101184977609161362375/photos\">aug4</a>"], "photo_reference": "CoQBdwAAAHZt8vKHUZzM-11YdB8juItz8WAhtQ5laM86wn7PxzDJ8zDf_zkUwGbceyvoaUIA1eNNun-8iFgMGac3a7D7XV9Nt9-KbHfXeBacG22vcu1C73vM933IMk-gbwsuM0JBJ7BK9FhCZ6QFLBSt0wHsnSIGdrqA57g-1sfk-TnBOsYjEhDt_Wb6tCC618vhAC3rSvCVGhQBCmMsneRneIo80G6aepTgH2xCsg"}], "types": ["park", "point_of_interest", "establishment"], "reference": "CmRRAAAAkh1WMFqBkRCU8Z6-qGjWZ39bADip0FsADA_vPytmBJ_f98h_oUeKkvGRBQftgvp3z7sB2uXufFlQX7qBI8xOQ2DE3aiyKZ5jDRrgIo2QRMGLIjOubcexO5l31g3Z9tkXEhALtVzGAahck8gZUu7vGwgEGhSG3KKSO_X24jKzSLE_ec4rpxFuyg", "name": "Willow Waterhole Greenspace", "rating": 4.3, "id": "0127506e8071350c2d48f0ca56e939045297a0f4", "job_title": "Surveying-%26-Mapping%2C-LLC-%28sam%29", "place_id": "ChIJR6_2zTzqQIYRsA7wExgfDWs", "address": "S Willow Dr, Houston, TX 77035, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.4003322, 29.7388505], "type": "Point"}, "properties": {"photos": [{"width": 1136, "height": 640, "html_attributions": ["<a href=\"https://maps.google.com/maps/contrib/117056878997299689379/photos\">Marisol Brown</a>"], "photo_reference": "CoQBdwAAAG2__Z94Ydu8HLZZnG0DjBNbqhd9nQlSfoYSPN06NN7NBI60n6UC7zN6a4ErG34rmW9IhMTLOv72rtW91Onc5xdAsmNGX_DcYzYvAD3v0nzTdY-gUzXQlB4wlNwEKGJnIoU5axu_YYufLxEKE6xiNDwG7T7Ilvnsd9ZFXRg6h-4DEhDqp96-dPwVmkBUibpWEN9VGhS3KjyM9J1s682y7rr6eUmxJ2stWw"}], "types": ["point_of_interest", "establishment"], "reference": "CmRRAAAAobh3wiSBBPB5_v56nsp9IOA8wHbw4JZKRQ9iP-xEFiBo0XBbvkfoyk07OsVxHR2Mqjn3jm5ruvvNC5uyvxknl0T5bAJpev8o67qoeRBfgnTUz4RTXLmCO8JZFyjvyJjbEhDXrIYEIqthnpsx5HEWPi-7GhTL04oSrX_-P8BQmyaNIwhcIXvTCw", "name": "Masters Fine Art Conservation", "rating": 5, "id": "a462c2eef4e22ea319485ae7b84f3d20756cbdd1", "job_title": "Surveying-%26-Mapping%2C-LLC-%28sam%29", "place_id": "ChIJp8u2bZvAQIYRbosnWz6cVmY", "address": "1612 W Alabama St, Houston, TX 77006, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.3876169, 29.794149], "type": "Point"}, "properties": {"photos": [], "types": ["art_gallery", "point_of_interest", "establishment"], "reference": "CmRRAAAAYxmb1GgGFiQBTfCOxymglCd0mUJ5_XXdRh0FkV1GZ5YnNx0Ldo1fwkLxOKQRoVWvriASvb6lqytzHGzPM8jo6Au_L3SGiW_YQI7fFTAlOkxrSi0OaxO76KN8piReXhbQEhB4GzGHuMTQhRpJdD-r2uq7GhSysBwidZRd1R3Llqp87BaBwk57uQ", "name": "Whitten & Proctor Fine Art Conservation", "rating": "NA", "id": "883a8c5ef35ab28e1630235ad65a6b16506a67fa", "job_title": "Surveying-%26-Mapping%2C-LLC-%28sam%29", "place_id": "ChIJ8YuXE6K4QIYRn1SF1hazFEw", "address": "1236 Studewood St, Houston, TX 77008, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.3858767, 29.7300997], "type": "Point"}, "properties": {"photos": [], "types": ["point_of_interest", "establishment"], "reference": "CmRSAAAAiFX6iPZVQq_et_btg7jFCRMUeIfJ0ICF5WkFH_M3NLxJV3jQ5RHYtYIzOloEbDYSTqvIYx5cofbOiopOtQ0MYlYvHM4aNYq_3Hr_XGlB7kXdvrQuV1qUJyVZLtnd_PwtEhDOHY0-hQ_SjdwSJ88QYc6KGhT4Bq8CTM3hZ4ZfHiuUHxn0uSLjXg", "name": "St Mark Fine Arts Conservation", "rating": 5, "id": "ea2d4bac6d74716b33f456dff3aae0cc0b43cca3", "job_title": "Surveying-%26-Mapping%2C-LLC-%28sam%29", "place_id": "ChIJKbDEoXm_QIYRcRFBlp0dE8A", "address": "4901 Main St, Houston, TX 77002, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.483218, 29.7482286], "type": "Point"}, "properties": {"photos": [], "types": ["point_of_interest", "establishment"], "reference": "CmRRAAAAxZH7dQanhrgrwAe6-PRP-5J4Hre2TbpXh540GW8J8cbANK-Mq634-nIVdLCGTqV4DXc3q1DgEtbTgjjWQ-GX_QtFZG_BFm9No-iKBLppZBVCMeS_9UwoB1wCQ7JiFPtMEhB3iP4pcFOq5Le22xOed9ZCGhTHdHSqpxNb6tkyp-IGMzzQ6OKaug", "name": "The Nature Conservancy", "rating": "NA", "id": "90af6fb9fb926dde9f7103577cebc4150bbb1dec", "job_title": "Surveying-%26-Mapping%2C-LLC-%28sam%29", "place_id": "ChIJq-m4EX3AQIYRJkn4Lhccp2E", "address": "1800 Augusta Dr #240, Houston, TX 77057, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.42318089999999, 29.7345943], "type": "Point"}, "properties": {"photos": [{"width": 750, "height": 437, "html_attributions": ["<a href=\"https://maps.google.com/maps/contrib/106788706324997826205/photos\">Erika</a>"], "photo_reference": "CoQBdwAAALXqupZFS6iTwfEfGjJAZ2WkXSm-7nveiScAVxeeVfsTp30_pOBnpiEbC8POzmO2e0nwby_n-sR46UBo99CaSuEjQU655og_GX7hgN73WRIeuI--ulHoiSW9LQlnrTqp-082ZgHhzjYxdkwLxDtGN_p0FuvCLQfvY6W-wxg-fUnREhCZizWdrbim_P4hJ4ay_GTxGhRDRFCVFXSLypFFbIFeZc5PaCwZ8A"}], "types": ["point_of_interest", "establishment"], "reference": "CmRRAAAAIGWzgm9CycK7OC6Sem9Z2gSDG2V87PrWO9ywgdkPyogFlwW0SyNth_tD9c4_jx2AwQS0fqkrCTh2Dt9VceufXqsLwc8xoK9Bg6OoIC2EMflZ9myjn65S8ISO6MO62ysjEhBpeo8IWuxpbYG_-Umda7BlGhQ7TXTkpaYFpcOi6nxGLlHwlZt1DQ", "name": "Student Conservation Association", "rating": "NA", "id": "1c5ea7722fc0d99e9f7dfca55f5d9078224d51d3", "job_title": "Surveying-%26-Mapping%2C-LLC-%28sam%29", "place_id": "ChIJQcqBXfDAQIYRErawO-goGj4", "address": "2990 Richmond Ave Suite #400, Houston, TX 77098, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-96.038102, 30.055621], "type": "Point"}, "properties": {"photos": [{"width": 984, "height": 985, "html_attributions": ["<a href=\"https://maps.google.com/maps/contrib/110279808588468038448/photos\">Peckerwood Garden Conservation Foundation</a>"], "photo_reference": "CoQBdwAAAHacFNBTnrqGgufxlpkoDC8eUJlUKq0kT8gFhKu1-OASsg5uoI7bI1EgNjDvSZDGX65TMOhOX0CdQjmbi7d7RUAVDa9rx88CigFYX7HcYwQxvAl4hRUu249muC3daWpSccXH-4_M7bijowprmpPTOu4ynDgZP6HVWdGRUXkMRxC2EhBPKI0eMfmiC4kgkK_2B3esGhRLfoaxuVIA7Oc7tVe2iy748VC_5w"}], "types": ["park", "point_of_interest", "establishment"], "reference": "CmRRAAAA2Wxaz44DDR51k16hLmWg5a7jhOF_TJntQKtLcMbs8U98OB31eWvS2nQLty43iDjK4a-3NSwB4nffIsy_DeLHpPOOvDe0AZsQQWwFn3Vm8czp3ZyaJLjQwcZA9lz1rLfmEhDhemHhXV_C5m_m6pluHjzOGhTQ_9tKaxpfjR7siyQif1Nz48-JSg", "name": "Peckerwood Garden Conservation Foundation", "rating": "NA", "id": "e618a4c618cd67ce4f5fdc165f640220ab3b53b2", "job_title": "Surveying-%26-Mapping%2C-LLC-%28sam%29", "place_id": "ChIJmUR7pvHKRoYRIIl0o73bPGE", "address": "20559 Fm 359 Rd, Pine Island, TX 77445, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.64386449999999, 29.7515036], "type": "Point"}, "properties": {"photos": [], "types": ["point_of_interest", "establishment"], "reference": "CmRRAAAAvUaxjAFVQr86V2o539vHUQReODqaWC1ffUurOdxHYzCjzym39a93Mmrc3ztsNg3oEWaULJd-MXc9QW_lhJdV3qeP4OuA4X7kOvsyQdMs8cPl5kHJKY_e6HB1itovA1K8EhBjEXlCVEr6RxeGBXm-GL-XGhThDgDWDCHV5T8eUr-DWxDIIumEGA", "name": "H2O Conservation Technology", "rating": "NA", "id": "30c07988ef8dfc62dac712b9d587daa4a36f2539", "job_title": "Surveying-%26-Mapping%2C-LLC-%28sam%29", "place_id": "ChIJIWZRKeHKQIYRXxta3wOMGGc", "address": "1725 Hwy 6, Houston, TX 77077, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.5705632, 29.7714443], "type": "Point"}, "properties": {"photos": [{"width": 3024, "height": 4032, "html_attributions": ["<a href=\"https://maps.google.com/maps/contrib/108143329814504597326/photos\">State from Jake farm</a>"], "photo_reference": "CoQBdwAAAId7qesA7x2tj82fJZsgwWyUe1GhpE3KoNDkqa8Osut-WFiPm8y9LAvW90HiGSJI0LtJ6lzin_vieC5GCjDnApI3G6mJpoCa3H4y_4f7q35k1CAq3dfm6-EA8g4Z_fxf7D70maxxFG9KMim5mYxVhakXlrtJ5TggCVTMAyzlEefPEhAHEuqmoRwhXy5YcUd1SfxiGhTTFkVEDwDWD0wfGIexn5doasN_bw"}], "types": ["park", "point_of_interest", "establishment"], "reference": "CmRSAAAA-KmbjfaHMSsKJ5cNrMS63PhrivbHpHfVUQoCEh_xmo7ZM94FF0nZQIevacntGcuyzw6LFimAPRjN-8WkbYdO0a82dQvpdcTfWqYRQIRbCR4VlEmjB-9_jyfchkHv77SzEhBgh79Iat8QlIInizTubNWyGhRivLLRCs0mfRqK4xqzlX2pMI4bAA", "name": "Houston Audubon Society", "rating": 5, "id": "050a5458d86bdd1cee7b09678bd6256d0a20a73e", "job_title": "Surveying-%26-Mapping%2C-LLC-%28sam%29", "place_id": "ChIJlQOxwVDbQIYR2uX_TZl0TYc", "address": "440 Wilchester Blvd, Houston, TX 77079, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.56820189999999, 29.770778], "type": "Point"}, "properties": {"photos": [{"width": 1800, "height": 1200, "html_attributions": ["<a href=\"https://maps.google.com/maps/contrib/108765250995932379967/photos\">Audubon Docent Guild</a>"], "photo_reference": "CoQBdwAAAKIZgNpwp3lDhAu22FjlHWrEgr-lQLLzrSCJuAk7IGkEXDVNfDG4jdutEkpitJqDUZPUZkR33YN0qa6kAOf0YDmOU1NabBAKqWFD6S8jfPEvZLS74g9xzJ1XF9rryCzvOfDlAvbDGeKX-6HmyATcRs1-9_tz_d27dTrDCGdLsEYKEhDCfytKxPbbbwPtGI8VDPSyGhRJ227VSyFfgKCmacHH-CmC85dgZw"}], "types": ["park", "point_of_interest", "establishment"], "reference": "CmRSAAAARiIpWGTIoLGYPMptgbOMKDUpwfRR4JSYl8Hru5K8aWW4Rs8DDh0Ad3M1G2AVnkO7MM_VmZUzK2dVHiAWZHyPQj_AduE5QrGBsvhxifIKdX_czIgJmXjyfKu3QGMTika1EhABLbiBEm-1_EOAhNno_GwWGhSupyuZ-5Ym2-508qtx5LhuIVgbHg", "name": "Audubon Docent Guild", "rating": 5, "id": "7ddd5daf76cc4979e2ba6b062322d1c77d5d1c07", "job_title": "Surveying-%26-Mapping%2C-LLC-%28sam%29", "place_id": "ChIJI9XyNFHbQIYRtwHb8EtTpeU", "address": "440 Wilchester Blvd, Houston, TX 77079, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.44932349999999, 29.7803218], "type": "Point"}, "properties": {"photos": [], "types": ["point_of_interest", "establishment"], "reference": "CmRSAAAAMeYQIkjm-nkN8-VmHmJKPeysHiexOfTedAxNiiu2Pk0ZH6sBKDqWm9wW516osqJmB2z9MpPaPfUoG8Aq110JucE4CJaihCV9imIqgRunRogpiWxqA-BAnl5CnPO40oGREhAG0Tr-xTbpbzX2hg0USW63GhRUl4ayG-0cq9d_JGhmQciiI8Vt0A", "name": "Coastal Conservation Association-Tx", "rating": 3, "id": "7258b034e119f31e82320bca6e72781ee9f79d75", "job_title": "Texas-Inpatient-Consultants", "place_id": "ChIJcekacM_GQIYRPzL13cgQrPk", "address": "6919 Portwest Dr #100, Houston, TX 77024, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.47039, 29.655454], "type": "Point"}, "properties": {"photos": [{"width": 5312, "height": 2988, "html_attributions": ["<a href=\"https://maps.google.com/maps/contrib/101184977609161362375/photos\">aug4</a>"], "photo_reference": "CoQBdwAAADXlysSefwTLg3_AoB1S3yNnx51sggnOtL2RNa6NC7p7wE2hWs3PylWseSGhbXl0nwDrCwgdP_stXJyTf_reyGZlWJmWt1pbIKDnPyBXUNj3vRTK6NLQGjnZVwpMBOD9j7eArZpu_D7WAQMrgp8Zia--JyTHNKjiTDc6gnsz4gmfEhCY3XBMGlQO4zbhsqlbObsHGhSUGYd97du_ZNAy44BU11vdWdRZmQ"}], "types": ["park", "point_of_interest", "establishment"], "reference": "CmRRAAAA1MNgvqOPmSrIbyLgOgAhVpibYY8ukcNhvSMzG1mphbJel__QWKswQIhAohWgH8ggVyzQ4SQjOPE1zXyDQj4LUt_RwKhb0wCcy8GjS3G7sQSSNNkQTf_8bpQdzSUhQkovEhCngmK_h4vqzconIpp-Qfg6GhSaNOewVlKUA1zzrWxuABtp0T6LkA", "name": "Willow Waterhole Greenspace", "rating": 4.3, "id": "0127506e8071350c2d48f0ca56e939045297a0f4", "job_title": "Texas-Inpatient-Consultants", "place_id": "ChIJR6_2zTzqQIYRsA7wExgfDWs", "address": "S Willow Dr, Houston, TX 77035, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.4003322, 29.7388505], "type": "Point"}, "properties": {"photos": [{"width": 1136, "height": 640, "html_attributions": ["<a href=\"https://maps.google.com/maps/contrib/117056878997299689379/photos\">Marisol Brown</a>"], "photo_reference": "CoQBdwAAAIEOzYkZXYwDzrKDZehxw7oH7heOAhu-oJzVV0gahk82p5n3C8b31qOMqnhvp9AZB1nFVRnXdEkj6RNe4bz61SibB7SEMdODgc7rHhSqW_a8iRWJkC8-gEFby8UEfklbSddOc3vhpXy1Xbk_2TL7TFFcUr54AOgLrvKiwZBnaN9tEhAf7tKePdXFtueobkOzDyCeGhQ6E1NMk5dhqf4BbsyucbX3QWcsTA"}], "types": ["point_of_interest", "establishment"], "reference": "CmRRAAAA9VOdhR2k0TyFOJB8nc1__vZzgSLi5VRiIAPLv2V-VHGRFSiq6SYf6WxoDpziLL-oBg49ZOh_NrbXlLX2dxcNqbFI9uNImo5V7ZokCYoYvHRTfMxDvhVTTjowPgpYBl77EhBiF9TM6hDYJrOXvmOf4IYuGhRVfOz0ut-RN5j_9AsziyOcoHwwiA", "name": "Masters Fine Art Conservation", "rating": 5, "id": "a462c2eef4e22ea319485ae7b84f3d20756cbdd1", "job_title": "Texas-Inpatient-Consultants", "place_id": "ChIJp8u2bZvAQIYRbosnWz6cVmY", "address": "1612 W Alabama St, Houston, TX 77006, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.3876169, 29.794149], "type": "Point"}, "properties": {"photos": [], "types": ["art_gallery", "point_of_interest", "establishment"], "reference": "CmRRAAAApSwodaRn2rbPb8e9Bv2TDvGjp6eXiynBuPKnNgwIot8PWjrkmDul4n5AquBiMGzkhy17EMUrF_m5kRL32OehFOpFQ587Mn8RU0OF0LX6yDxM90ijPD9ZF-dli5IZC-0QEhAy0Vj5xyKHlM7ihVfW1RRfGhTdeleM_ROo5FAH7b9HKNGlysVo7Q", "name": "Whitten & Proctor Fine Art Conservation", "rating": "NA", "id": "883a8c5ef35ab28e1630235ad65a6b16506a67fa", "job_title": "Texas-Inpatient-Consultants", "place_id": "ChIJ8YuXE6K4QIYRn1SF1hazFEw", "address": "1236 Studewood St, Houston, TX 77008, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.3858767, 29.7300997], "type": "Point"}, "properties": {"photos": [], "types": ["point_of_interest", "establishment"], "reference": "CmRSAAAAeSRckqVrA-aWq3vdQfkGJQsw68WgEIPJIbm_r_GZy5Ze8Odh9Z4skTeJ6T2pzLjBgXKG1L9aBxHkLjUjGiWHmrx37oST8sDYPOXMjmsWph2VHOe-BZoX0QF7oBIfQ0mDEhBVmmDRSP47JVvz01YhI8ewGhRgougCO1KxhNs31Dh-MeEJySZiZA", "name": "St Mark Fine Arts Conservation", "rating": 5, "id": "ea2d4bac6d74716b33f456dff3aae0cc0b43cca3", "job_title": "Texas-Inpatient-Consultants", "place_id": "ChIJKbDEoXm_QIYRcRFBlp0dE8A", "address": "4901 Main St, Houston, TX 77002, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.483218, 29.7482286], "type": "Point"}, "properties": {"photos": [], "types": ["point_of_interest", "establishment"], "reference": "CmRRAAAAY9WjMbS2Kofg1-wFeW2dyE7SwPnz1nPh3naKUbad0sU7IU0qRm7Ki3B2FMM6jGo2gr8XyoKxsg0JBwU5bH2vZT_rgw7mXC4j8R0hNpo_q7o9Wm5A6myffKQIS7OWbZTOEhCiaRRb53UPPiMP15wVD8efGhSm_MYmubIy6DwPgv7CtZB_cuVxSA", "name": "The Nature Conservancy", "rating": "NA", "id": "90af6fb9fb926dde9f7103577cebc4150bbb1dec", "job_title": "Texas-Inpatient-Consultants", "place_id": "ChIJq-m4EX3AQIYRJkn4Lhccp2E", "address": "1800 Augusta Dr #240, Houston, TX 77057, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.42318089999999, 29.7345943], "type": "Point"}, "properties": {"photos": [{"width": 750, "height": 437, "html_attributions": ["<a href=\"https://maps.google.com/maps/contrib/106788706324997826205/photos\">Erika</a>"], "photo_reference": "CoQBdwAAALiPzgR8BkbtpGTly_hz71M0-fSz6Hko9v7zU-rEKo3z67nMuJyc2Z5aCQZhP98f5aWY6QEKBMY9PcqS53HmB19tlf_3gTKIU4mBY7gjaJ6HkBFoyxhczmQ42HXcGOIws_cAIr3fuaH2a4CXGaa-CCqVmvxrfs7ymSQxy0ObeyLUEhBPf18SmELwqTJlca4QQrizGhQdnUpYG8Cduclb6W2Kh4190Zf0Hw"}], "types": ["point_of_interest", "establishment"], "reference": "CmRRAAAAEDlxRDBYyvcl-uMj9JhdCuNoXnTTtpZrNRgqEVu-y2GTBLaQ4moopFhagql_EjiPsBcMJl3tp7NB3cAMIiGXW6AgBT9H5GgAiKFjmU1AHVh95fTydRE0wQLSt-ZWS1R7EhBzOIqWHMj1S93GZdQ3rzKVGhQBLrTanS4PwK_lgSnejQsnGvLMPg", "name": "Student Conservation Association", "rating": "NA", "id": "1c5ea7722fc0d99e9f7dfca55f5d9078224d51d3", "job_title": "Texas-Inpatient-Consultants", "place_id": "ChIJQcqBXfDAQIYRErawO-goGj4", "address": "2990 Richmond Ave Suite #400, Houston, TX 77098, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-96.038102, 30.055621], "type": "Point"}, "properties": {"photos": [{"width": 984, "height": 985, "html_attributions": ["<a href=\"https://maps.google.com/maps/contrib/110279808588468038448/photos\">Peckerwood Garden Conservation Foundation</a>"], "photo_reference": "CoQBdwAAAGHcYaPUNNpVtPWjyPpp14m4gJgMNHXIvguo6Zr6zhORvZe1z0DSj-aOy_y1gGAgv23IAAGGv50-neBOQj_FGWvYf8Xa7OICmsXEJB5UqTm04TouWlKrxd-1mkS3BV30MvDl1cCHaBEDvXTaSDuXDGB6uHEN_yhU5HGUzmagH5iKEhBSaEDm1LbQcXOiHx7lEhWFGhT9uIisN66oO5CStOXsdHzhrIwtdw"}], "types": ["park", "point_of_interest", "establishment"], "reference": "CmRRAAAAeaXkJ1HNtyRn7cSURDOpBdVr31Zzg4WFqPmzuEXZPDJHhPEyKmy5KIlgLKbZ8_JaOpHzhE-ulfDGHkpcWHiDN_cIO-98bJ-dDh0J7rsjNvb06DAlSuY_ATziChAxZ2asEhAtme5thnMHZ6oRlt22l64kGhRmLGjsE_3ov97l-hokAKts53-Vtg", "name": "Peckerwood Garden Conservation Foundation", "rating": "NA", "id": "e618a4c618cd67ce4f5fdc165f640220ab3b53b2", "job_title": "Texas-Inpatient-Consultants", "place_id": "ChIJmUR7pvHKRoYRIIl0o73bPGE", "address": "20559 Fm 359 Rd, Pine Island, TX 77445, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.64386449999999, 29.7515036], "type": "Point"}, "properties": {"photos": [], "types": ["point_of_interest", "establishment"], "reference": "CmRRAAAAzjVz9CmlQhJdewtvl9rU2kDoqCUw9L_3CK8wX5y4AHvuEhK67SWvEIeDKTPk4Hix-g-xIhKouz9WsYFduA1MbNoJ5mvYMICrbZhhYEYFmsgrdqP6tZWMtBsheyhj9hTUEhANcDqJF3lr5BH7kc1yDcXTGhR-Ad8dmBDhwb9SGXYNzKWzLrqTww", "name": "H2O Conservation Technology", "rating": "NA", "id": "30c07988ef8dfc62dac712b9d587daa4a36f2539", "job_title": "Texas-Inpatient-Consultants", "place_id": "ChIJIWZRKeHKQIYRXxta3wOMGGc", "address": "1725 Hwy 6, Houston, TX 77077, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.5705632, 29.7714443], "type": "Point"}, "properties": {"photos": [{"width": 3024, "height": 4032, "html_attributions": ["<a href=\"https://maps.google.com/maps/contrib/108143329814504597326/photos\">State from Jake farm</a>"], "photo_reference": "CoQBdwAAAKQSbBARbPzGhzYOvbrlD0KP-CGpRKLwu_JbGaa58E-iMEtp1UQt2rvaBHyorK0nE3E85DTi8y7pNwbO1ZztCXY3nBZ1F_HAHz4QNwN-0SqHitJIaINZjR-zn8aW7gNGJi86TKfduwK8vVgSG3mHyUB6fcGqlHJ0CZdXNP46-C8EEhDpV2kAZWfxD5ZerwP-wYy9GhSvD-7r6ggRwqe8Ppq0vo2NrH2Paw"}], "types": ["park", "point_of_interest", "establishment"], "reference": "CmRSAAAAA-suP74ibg-f89gNrLb5Dfg5ILa5GJ68aV-gnU21WMno3cikfOkfWTu6ldy8eErOLpmyKJc7mzjt97UAiK0Ozw1D7brzEL-OpX1WKQI8a8DuS1HEfY6QmeHKpMQByqLpEhDoH5CUrGrdKU9nCF0e-_9bGhSPyWHtHxSNGdopEFliinqc7KU73Q", "name": "Houston Audubon Society", "rating": 5, "id": "050a5458d86bdd1cee7b09678bd6256d0a20a73e", "job_title": "Texas-Inpatient-Consultants", "place_id": "ChIJlQOxwVDbQIYR2uX_TZl0TYc", "address": "440 Wilchester Blvd, Houston, TX 77079, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.56820189999999, 29.770778], "type": "Point"}, "properties": {"photos": [{"width": 1800, "height": 1200, "html_attributions": ["<a href=\"https://maps.google.com/maps/contrib/108765250995932379967/photos\">Audubon Docent Guild</a>"], "photo_reference": "CoQBdwAAAJFcebVRHEDoFgCBjsVfYReHWKDo0Msl9jL3vUm6ZIZawRTEHT03OxhkytbB2W8VK86xixDrEdCliH6BMNBgkC-qzzCBWPNwbmuGa12EU4VE8O1HsLMm8rcjLKcvEzQ1YSVYtJu5n6nQONh0et9ViwFcX1NtMXlwC1cyt_21vNcFEhBPDEIHdJDfzGAFkeNLkMyTGhTDB20kGXBGS61lI7PxFI8ECcx3nA"}], "types": ["park", "point_of_interest", "establishment"], "reference": "CmRSAAAAf8VaqguBgIUkD11Fq9cBequ75FNpU_WshErat5LkEyPY7nuYRlCS0Frs1CoIENoiud1thnr-uvM60qxP4ipegfhyzgnaD2RWKAYsKWF1vSXxuQgyPA1nkeRX9tQUXZSTEhACQjVw0out-NOWz0o56YTAGhQUYKNDcE6AYX-yYpamagp8xZMcdA", "name": "Audubon Docent Guild", "rating": 5, "id": "7ddd5daf76cc4979e2ba6b062322d1c77d5d1c07", "job_title": "Texas-Inpatient-Consultants", "place_id": "ChIJI9XyNFHbQIYRtwHb8EtTpeU", "address": "440 Wilchester Blvd, Houston, TX 77079, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.44932349999999, 29.7803218], "type": "Point"}, "properties": {"photos": [], "types": ["point_of_interest", "establishment"], "reference": "CmRSAAAAI-RUAxVsy1Zi4B742n9nLgIeaVqHgaG5YY0b3yjh2kZgWbjUwCzAD2nUZv2dDIAhjZkU0OsoLNzOrpBAAn13lKKojv3H6j4kGg9KifnTA2NlpQQOM14nWan7ZEEhotzPEhA7pOvEnr_opm0rf3T8jy66GhRdO--xXA_AHylZ_r6dN6ah2OU2Ig", "name": "Coastal Conservation Association-Tx", "rating": 3, "id": "7258b034e119f31e82320bca6e72781ee9f79d75", "job_title": "Prosperity-Bank", "place_id": "ChIJcekacM_GQIYRPzL13cgQrPk", "address": "6919 Portwest Dr #100, Houston, TX 77024, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.47039, 29.655454], "type": "Point"}, "properties": {"photos": [{"width": 5312, "height": 2988, "html_attributions": ["<a href=\"https://maps.google.com/maps/contrib/101184977609161362375/photos\">aug4</a>"], "photo_reference": "CoQBdwAAAIHZcjoVomYl8YvliFxrYYsVRrHj9Od7znZ5YHuQAQwN6Ryrdg6SJsMNSI4kkmijBJM3otrniNIIPA8E1eDhJ1BDVoAzf_uNMOczFHoj4ohRdOFVDbxEJ1HftPDO5xZXBCyVC2jFUscrgUQrusdRZ67zy6zEr1mcJyinP8m-_wSHEhBhRcaz7ig3olkgM2BbKkIQGhRF1dFML51lPqY61kuZ7EEqihwEuQ"}], "types": ["park", "point_of_interest", "establishment"], "reference": "CmRRAAAAviU_TuRk1UX0-xAOdUeN4ZSc6ToZbMCEoHiqHFsIqxiXvMHbtWcVsRoflcfx0-Nw3F-HetDE709asoHEqdJMGMHcI1beyeh7tOziJRYSroh6C0z-Nz3DirYaNv9p8WLmEhBi6LAsXumx80lZMtMslUDbGhTofHA7ZUWpkAMgKA93vOMiHIOLKw", "name": "Willow Waterhole Greenspace", "rating": 4.3, "id": "0127506e8071350c2d48f0ca56e939045297a0f4", "job_title": "Prosperity-Bank", "place_id": "ChIJR6_2zTzqQIYRsA7wExgfDWs", "address": "S Willow Dr, Houston, TX 77035, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.4003322, 29.7388505], "type": "Point"}, "properties": {"photos": [{"width": 1136, "height": 640, "html_attributions": ["<a href=\"https://maps.google.com/maps/contrib/117056878997299689379/photos\">Marisol Brown</a>"], "photo_reference": "CoQBdwAAADWIueAuQT8UWFnuHAA6CUPEwYbAxX0wwxjR2blUydrVcdvzDY0-2zm3kC7XrnG6CZAN0yZfBTITHrKxL3_QLRGs1IpllGGHJ9ccfNigZw3QMmzVCCm67cUIFu746SLXkHkAz2Ffo2oMSns36HDqBp_jkwiIIi5XuutPmkGmFJ8PEhBVp65Nl5fd_gwoLovgeBhyGhSQeA2E3tKSPydRyRDrm9J8UV_S2Q"}], "types": ["point_of_interest", "establishment"], "reference": "CmRRAAAAcIkT2ahYDvGX3w84Xb8c1SAuEFLRhTGjvBkWHsFr6Vm-NSQqKZPA3APWpjS55-wUV4tnmc0PXyuJ-cqLT07WqaDFruNw4ijX3U2hnUNRPzDwQXaiSbVBaaADWbqvVy1wEhBP0yj0QveniZnfXzjPmOqpGhSw-3DKDwIkl8uJhFu8nBb5bq5Rlg", "name": "Masters Fine Art Conservation", "rating": 5, "id": "a462c2eef4e22ea319485ae7b84f3d20756cbdd1", "job_title": "Prosperity-Bank", "place_id": "ChIJp8u2bZvAQIYRbosnWz6cVmY", "address": "1612 W Alabama St, Houston, TX 77006, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.3876169, 29.794149], "type": "Point"}, "properties": {"photos": [], "types": ["art_gallery", "point_of_interest", "establishment"], "reference": "CmRRAAAAcPUKMLmgniI5K53EsOTJxDRCCZrA9QASbATDip2r_yWvgQux-rS9kTwbwWw85YkjDI1kyH3EECQKjfWnRDSuBTzjES1lVRyRGV1_C4oEr239iFOFVB9XW1zD5-fCeTUqEhCFwyyvNq999TOvbcBnxgT-GhTHMnTvuVzNHiofBnfqfE0pBI_thw", "name": "Whitten & Proctor Fine Art Conservation", "rating": "NA", "id": "883a8c5ef35ab28e1630235ad65a6b16506a67fa", "job_title": "Prosperity-Bank", "place_id": "ChIJ8YuXE6K4QIYRn1SF1hazFEw", "address": "1236 Studewood St, Houston, TX 77008, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.3858767, 29.7300997], "type": "Point"}, "properties": {"photos": [], "types": ["point_of_interest", "establishment"], "reference": "CmRSAAAA1-tXd0bX-Pna1ZdXHvPDtxLHUPDcf_PIX9_-jFZ2xFjtRkIZIqm9RTaFze6T3b5FSe428ZvfWT5QEZnE5iaCN3RA87QFo-nuB1vIJQMXG0t4ISsLkKpqr-4jOCzmoPbREhAh5jVyj29ut-cGXNrMsRZlGhQyfNCkj91fNNSwtXtdBHNZY5sFqw", "name": "St Mark Fine Arts Conservation", "rating": 5, "id": "ea2d4bac6d74716b33f456dff3aae0cc0b43cca3", "job_title": "Prosperity-Bank", "place_id": "ChIJKbDEoXm_QIYRcRFBlp0dE8A", "address": "4901 Main St, Houston, TX 77002, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.483218, 29.7482286], "type": "Point"}, "properties": {"photos": [], "types": ["point_of_interest", "establishment"], "reference": "CmRRAAAAXEnHjrSFIE-5h8ZRVudZEn-7Kl2aQkozYbpBv-ZT5487ge_ubY3GZX91aalnfSQaJkFxoQRxiXTyk5bBCRIXfxcwLBaHbA4ZAW7ooCSAAHcqwQVHWpW7YLww68jTZ0CgEhBzyo2C-83bIlM-SM5aiVnDGhRm6C_hUz5ph23O4wUyqQdHPIvjsg", "name": "The Nature Conservancy", "rating": "NA", "id": "90af6fb9fb926dde9f7103577cebc4150bbb1dec", "job_title": "Prosperity-Bank", "place_id": "ChIJq-m4EX3AQIYRJkn4Lhccp2E", "address": "1800 Augusta Dr #240, Houston, TX 77057, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.42318089999999, 29.7345943], "type": "Point"}, "properties": {"photos": [{"width": 750, "height": 437, "html_attributions": ["<a href=\"https://maps.google.com/maps/contrib/106788706324997826205/photos\">Erika</a>"], "photo_reference": "CoQBdwAAAK8tgr7S2ZisIzcF1cPDE79QZvg6oQhhUjVOXfdSH7l3QBg40phvWOm5BRBXlmTlRvp5ckrxIjDG2LKdlxVW_aRac4NARbsZAt2XiSPOqDqnnDBdnaLqJZ0-UxbhzwNVVkO8xka2Gwi2usdZwr9c_oSeR-KmInmFvqicf8siFOQgEhCf3hWgWef13AA3k7bicj5-GhRmRfXyDxbHpBpDsfL0KwLVAP0zkA"}], "types": ["point_of_interest", "establishment"], "reference": "CmRRAAAAteGiWmDtp9s9vD3KdW7hX_eyGQzzPu3Q1xd423HSVcMSkLsph8URio18pen6jy4xN0qZJfsaQJ6Ia4kWZXXa0WJNz0qPrsM_5CFp_OPkOFK2fSVsrxVX_b9f-l60VwOiEhDTKOl6Wmy_rLJNONhYFgxNGhQeO9Weem95g6Q6GGPcqiec2KAwbQ", "name": "Student Conservation Association", "rating": "NA", "id": "1c5ea7722fc0d99e9f7dfca55f5d9078224d51d3", "job_title": "Prosperity-Bank", "place_id": "ChIJQcqBXfDAQIYRErawO-goGj4", "address": "2990 Richmond Ave Suite #400, Houston, TX 77098, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-96.038102, 30.055621], "type": "Point"}, "properties": {"photos": [{"width": 984, "height": 985, "html_attributions": ["<a href=\"https://maps.google.com/maps/contrib/110279808588468038448/photos\">Peckerwood Garden Conservation Foundation</a>"], "photo_reference": "CoQBdwAAAFuu_bbKOTFHEFDH6aLWuP8bt4TbM6-moMxPXLWmShv2vtJwgLFYCOw8xTL-Xu4Nkcpq_zdrWYR2pzGyovQkizMQunuGZHoHpPaL0iRkihrf-h8Nn56xxoA5e9qhDHzDKkRWIvJII3qaURVh-ZT0AY2zVndvmI9VWNYO0HMLobpdEhCCMAiElqAFAO5RHdvpQCD3GhT8zBHFdOz7cSbVYz9vEPxfHtT_LQ"}], "types": ["park", "point_of_interest", "establishment"], "reference": "CmRRAAAA3WGCMguX32neqyQOg34SnS7g_9hkjv2o5DTeBvIM9cG_MsolyvhS0zmoGzvqgN8OjYnfd277ue_0MZ-zGFnhZ2BwLuQ0ykDMZh1N1XZsrqYF1Kwo90k44Oc6-cRraKgHEhBb0uQXyYafc_u06NwluD0kGhTtoiXzYx2e7WAo98CleUk_YgGg9w", "name": "Peckerwood Garden Conservation Foundation", "rating": "NA", "id": "e618a4c618cd67ce4f5fdc165f640220ab3b53b2", "job_title": "Prosperity-Bank", "place_id": "ChIJmUR7pvHKRoYRIIl0o73bPGE", "address": "20559 Fm 359 Rd, Pine Island, TX 77445, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.64386449999999, 29.7515036], "type": "Point"}, "properties": {"photos": [], "types": ["point_of_interest", "establishment"], "reference": "CmRRAAAA_FjYCzBlbywdIYAjnnqR3tQ42vDheSwQeGdPHbVY37NsHjG5oa3HOBf_8cqJFeXyhQKu05t74yzza-y9QTP0FZSSYrABZxggD9k-Y5wNzbqBEKh_1IKlqiGT5K-q9fyWEhB50EJy1gB9SRf_1cyoUxU_GhTInCobvGMaq3XXO7wOhyseMqW5EA", "name": "H2O Conservation Technology", "rating": "NA", "id": "30c07988ef8dfc62dac712b9d587daa4a36f2539", "job_title": "Prosperity-Bank", "place_id": "ChIJIWZRKeHKQIYRXxta3wOMGGc", "address": "1725 Hwy 6, Houston, TX 77077, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.5705632, 29.7714443], "type": "Point"}, "properties": {"photos": [{"width": 3024, "height": 4032, "html_attributions": ["<a href=\"https://maps.google.com/maps/contrib/108143329814504597326/photos\">State from Jake farm</a>"], "photo_reference": "CoQBdwAAAC7d2koY1cjnS4ytIAHs9ujVhmdbKO9FZRAHImPBdFOtda41_IjDToN_R5oFLRUlXAgZUg67krOKLRONhXDuW4Kq8ChxBwsoRYnLJ5rKSgdRy5DgEwAeKbzWOenH6TzzuQXQqPF-5cUqHh42a1R0XU2mXOdrwXmdJESoeE1P2zxTEhDkmEhP1tHFA0RgycOwQ80mGhTTMBZVaKcHK_G7xMFY6AZqeW0T4w"}], "types": ["park", "point_of_interest", "establishment"], "reference": "CmRSAAAAdRXH8jsdA_0dTe143zJtB0QKy4CiRxHWUtYo0MojDOFzntnc6zrRnFX-BniGgYOzoUu0Y_rjzX6vouYk7As9KEHAXdvYCMLTgeYsE61YMwfrNT_WuTi9KzPT6fbXM85FEhDbmgUxgaQPESpnytZtorpqGhR9fy4LzZkU7k6YHu51T4HUln-B0g", "name": "Houston Audubon Society", "rating": 5, "id": "050a5458d86bdd1cee7b09678bd6256d0a20a73e", "job_title": "Prosperity-Bank", "place_id": "ChIJlQOxwVDbQIYR2uX_TZl0TYc", "address": "440 Wilchester Blvd, Houston, TX 77079, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.56820189999999, 29.770778], "type": "Point"}, "properties": {"photos": [{"width": 1800, "height": 1200, "html_attributions": ["<a href=\"https://maps.google.com/maps/contrib/108765250995932379967/photos\">Audubon Docent Guild</a>"], "photo_reference": "CoQBdwAAAGJB3ji80aY9kqcARO0Oe-kI74sbe7LnS5MTwxHiumOygd2rVfi_M-IksX0pbSEBugMnw2GJKZG-54ewKi5i0L_sk3IgU49Q5LP9MHOXLPN_3VVopnxnE7NvJw77FG8V3QW3QR1axKxEw2v5G1LtVfTsmLzpnFKfU1o5WN7IUArwEhBQ9qo2dFzLFoK-LCQL8y1jGhTTLff-uXtfKq5GhzoDs5quR0Rv6w"}], "types": ["park", "point_of_interest", "establishment"], "reference": "CmRSAAAAPsmAG9Eb6fZbMMUi2reMsVmPFQ27hHRnsIcJ4ujAuwH5kgMh8ItbRLM8vzJFdlcXq3S8DtC0yL77LRzVYjHUqLn5ZpPomPReWldItyPPGg1NohHL6OeElWihQZ-6WRO0EhB16rNr2i8HEvaxoW2LNyOfGhSwAx7YZro_dsLsNr9Zz2VolwxYJQ", "name": "Audubon Docent Guild", "rating": 5, "id": "7ddd5daf76cc4979e2ba6b062322d1c77d5d1c07", "job_title": "Prosperity-Bank", "place_id": "ChIJI9XyNFHbQIYRtwHb8EtTpeU", "address": "440 Wilchester Blvd, Houston, TX 77079, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.44932349999999, 29.7803218], "type": "Point"}, "properties": {"photos": [], "types": ["point_of_interest", "establishment"], "reference": "CmRSAAAAIW7nHTi51TkRc6-JiNsLerrS4mWcT4x0gQ_zqdWifjq26oB_m5HBRr4C7N5_5UHQ8wkTMZ9pc8PJDy7ECg45SQfzCTUNoIVhnGSieaGSet09n1ch5gr5jaFXoEeNajSuEhC_7b426j3uLNHvfdOQNzKvGhSy0glGAj1gfNpwcy8agH65VgdD2A", "name": "Coastal Conservation Association-Tx", "rating": 3, "id": "7258b034e119f31e82320bca6e72781ee9f79d75", "job_title": "The-Nature-Conservancy", "place_id": "ChIJcekacM_GQIYRPzL13cgQrPk", "address": "6919 Portwest Dr #100, Houston, TX 77024, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.47039, 29.655454], "type": "Point"}, "properties": {"photos": [{"width": 5312, "height": 2988, "html_attributions": ["<a href=\"https://maps.google.com/maps/contrib/101184977609161362375/photos\">aug4</a>"], "photo_reference": "CoQBdwAAANfLdOqcPuGaoI_TzKJ-cYd-AovaO7aWMFDCdwJhwZEmaqBR4zhVDFqowKo6-TfHiOakflzzUmoRyvxKh3hpioyQb1OBoWn6WzR5N8nXd8kRizcBSxGQ1WpiQWD_e9RRTqRE6s0x8MMMySSJcct28lPXjlUtlhximBnnGowoythuEhDlF9Mw-xJ3reccrAoD4ImZGhSh9BXTn5bPjSwBk4DES4Kgki0QMw"}], "types": ["park", "point_of_interest", "establishment"], "reference": "CmRRAAAAjxg5fIpxFkNOSES5i1CPhIVX_SzzxJk76nH1Tr9ra2Hqnz-qsMsNk4UcKkZB8-FdxM6vPClIPpjr-APcTWG8iMVeywiskuleRR-MSv2NoFVh3BdDiyDYY-aa1T3dH_o7EhD9g7Gkep6Fsw-LfWXybtMJGhQ4x7ZTdBbMqnYwmF7jjb9yG3Nxxg", "name": "Willow Waterhole Greenspace", "rating": 4.3, "id": "0127506e8071350c2d48f0ca56e939045297a0f4", "job_title": "The-Nature-Conservancy", "place_id": "ChIJR6_2zTzqQIYRsA7wExgfDWs", "address": "S Willow Dr, Houston, TX 77035, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.4003322, 29.7388505], "type": "Point"}, "properties": {"photos": [{"width": 1136, "height": 640, "html_attributions": ["<a href=\"https://maps.google.com/maps/contrib/117056878997299689379/photos\">Marisol Brown</a>"], "photo_reference": "CoQBdwAAAM4eIor82AX1KkFih9xeU4reVX842Ee6vJMLADYBKWs7uniLUd8VYmtGFsSlpphShC8z63kHci0nHy9RAxSDj3Gt-J8QHk55SW7IjKuDzmUvq_PZcDhZ4mSSxE07dB5-Blse1mblFp4aNg-J0RSclA5FMAmav3zFzjgsd6Mg8vDAEhBpSQxk4dDMLWj8wdy9GDe0GhREHMPx8KsWGomSmGtZNahRnCzAyQ"}], "types": ["point_of_interest", "establishment"], "reference": "CmRRAAAAAhoG2j1DrZge6Nu95Zb1VPma6r5Q8ZGbJuCjRIHXodvhQzvLxNcrhb3xGoT2MWBmG-DoT1_l6dGhm6j8r45UcQDxkwXxgGVPcHlu7KAqMZlpMcibV2h82yPDCnEc_4-1EhDxQ1HdCMdW3_08ZhblPaT6GhQjI_yQkhpW4nWNGuJ33A-nVTnnqg", "name": "Masters Fine Art Conservation", "rating": 5, "id": "a462c2eef4e22ea319485ae7b84f3d20756cbdd1", "job_title": "The-Nature-Conservancy", "place_id": "ChIJp8u2bZvAQIYRbosnWz6cVmY", "address": "1612 W Alabama St, Houston, TX 77006, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.3876169, 29.794149], "type": "Point"}, "properties": {"photos": [], "types": ["art_gallery", "point_of_interest", "establishment"], "reference": "CmRRAAAA6vikfFKjrzZWSUsGqLA3JfClQMV5s420mqxbAOXTBOj3sJzQhpPsI5JMacTrEuo7LtomAweoilI8vJfASdSNDGv-Mz2a4Gt1VeXyFlObizxKrQ-LOXydnvEXHtrXa7zvEhAckuER1EmEPBr430aLxgIBGhRuwPpSm7kh94RKsQlawmmqSQ6W6Q", "name": "Whitten & Proctor Fine Art Conservation", "rating": "NA", "id": "883a8c5ef35ab28e1630235ad65a6b16506a67fa", "job_title": "The-Nature-Conservancy", "place_id": "ChIJ8YuXE6K4QIYRn1SF1hazFEw", "address": "1236 Studewood St, Houston, TX 77008, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.3858767, 29.7300997], "type": "Point"}, "properties": {"photos": [], "types": ["point_of_interest", "establishment"], "reference": "CmRSAAAAkkFmnG9aVw5ndtMvpLOYDyjYOJwH0CVe3aQNB3PUczQKdgGgCCqWQ-Sk_8zEQt87ByH1LQTtvBCXV4BNWnc4OUs5VlWEs5xV-UJAHr047_ZZ9NVPszUqAfac4yc66g_7EhCtncZszSZ0q8HCd3u5_gtQGhT9Gvk9ahqZkhvxQysrn_bwuJeHlQ", "name": "St Mark Fine Arts Conservation", "rating": 5, "id": "ea2d4bac6d74716b33f456dff3aae0cc0b43cca3", "job_title": "The-Nature-Conservancy", "place_id": "ChIJKbDEoXm_QIYRcRFBlp0dE8A", "address": "4901 Main St, Houston, TX 77002, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.483218, 29.7482286], "type": "Point"}, "properties": {"photos": [], "types": ["point_of_interest", "establishment"], "reference": "CmRRAAAAwNHQroPtMphB-Ex_rTUdS3q5lTJ44iq9iunV4wHdFSrpoL9RBBLBHbVIzCEm2e4ferfmrVcKDdvBCdFweiTS2T6_W2g123Th4VRVSCnHs2DAS4uvs8vybHJrUMDIkuyOEhCIWQDxBCN0Vgpl7eGi1j1XGhTH0bshLUYZaO3NgCTAoDQWoMI6Aw", "name": "The Nature Conservancy", "rating": "NA", "id": "90af6fb9fb926dde9f7103577cebc4150bbb1dec", "job_title": "The-Nature-Conservancy", "place_id": "ChIJq-m4EX3AQIYRJkn4Lhccp2E", "address": "1800 Augusta Dr #240, Houston, TX 77057, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.42318089999999, 29.7345943], "type": "Point"}, "properties": {"photos": [{"width": 750, "height": 437, "html_attributions": ["<a href=\"https://maps.google.com/maps/contrib/106788706324997826205/photos\">Erika</a>"], "photo_reference": "CoQBdwAAABqSaAIwEJIOkDVlRTAXj1gbC7VEhddu-Hc8fF54xL805E1eo8sGQJ0XSnLSRPsQXUKGtQWPlKYh9tDQFJ5u2i_biqL5vH5QDRkYK6PoRMzMcIY4svOsvopUSU8FWBJXdk5qQ6IDm9-vw44dLwgZAZgVk6hyUJN79GGuo950jL8SEhChHIJMx6A-tlXI6yw2-2acGhRhuY_EoEL5bXNsYeXKnd1sRPHMMg"}], "types": ["point_of_interest", "establishment"], "reference": "CmRRAAAA5eqy_st9aDmi3w5e4tgTSBfGEckgCfGe2shQ1kPwDOthKF_vsFl1hm2WgXfpdvjpwQwLoFqnp4-OWiT7-u25WEcQcDUlwrl0DVe5yR96DPHMYJQU6QdpNE-PDO0IN4JfEhB0tcyIMJ6bT6HHiCSXJZjJGhQMxPci_T5XULf15kXqoJmonnlpvw", "name": "Student Conservation Association", "rating": "NA", "id": "1c5ea7722fc0d99e9f7dfca55f5d9078224d51d3", "job_title": "The-Nature-Conservancy", "place_id": "ChIJQcqBXfDAQIYRErawO-goGj4", "address": "2990 Richmond Ave Suite #400, Houston, TX 77098, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-96.038102, 30.055621], "type": "Point"}, "properties": {"photos": [{"width": 984, "height": 985, "html_attributions": ["<a href=\"https://maps.google.com/maps/contrib/110279808588468038448/photos\">Peckerwood Garden Conservation Foundation</a>"], "photo_reference": "CoQBdwAAAKsP7RGQWpODxZmbOi-UNbH8a5wJH9eC0tJm5wcgEz1Liw3LSmkXcm3T_jkiGoZGuG58F999axxS9GtcdUPbrJ8559V7NYPczw5DkDl5NzEfaO1Wo-b-RkaP0ONKURZnaUZfsHCrn-4osDpakG7wYTtIS68lRXBRkmONqWa1jaYBEhDKXoKz2cgMWb1yfKXgL2HvGhRcwuLnLHA_S1bA6WsSATveStoMZQ"}], "types": ["park", "point_of_interest", "establishment"], "reference": "CmRRAAAAWpx8kUuUeFk2xpmsbUQ3CzRwHFcyh2FjXPh6BQBYYMIiwc-9lBH3g92pKRxE0DEPtGLM3tzbmRCDzLt9UEkgxE5-l7CPtoZk05j8SHfLABaBwix_xZwEov8v6tuutRlyEhAabyyJuqKhApL5D_g1Q9v2GhQzpTnQeUd62fWZYIwsX8xDkuHPzA", "name": "Peckerwood Garden Conservation Foundation", "rating": "NA", "id": "e618a4c618cd67ce4f5fdc165f640220ab3b53b2", "job_title": "The-Nature-Conservancy", "place_id": "ChIJmUR7pvHKRoYRIIl0o73bPGE", "address": "20559 Fm 359 Rd, Pine Island, TX 77445, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.64386449999999, 29.7515036], "type": "Point"}, "properties": {"photos": [], "types": ["point_of_interest", "establishment"], "reference": "CmRRAAAAnMFEFeJEgHgTcf_wfUzKqFRCugHej-bxTpctWDSGJBI0BjhrvrnhasI5x3LcJfn_GnX2Xzx5x217naKAIZleQIy_3aPL1hqr4gKNJ-tP_tbabJHq_EtxEJ6dkdfL4a5PEhCaz9lQLVYxKeXMCpZiZPROGhSPczUVB1_A0-y4_IoLEpaPHjnEHw", "name": "H2O Conservation Technology", "rating": "NA", "id": "30c07988ef8dfc62dac712b9d587daa4a36f2539", "job_title": "The-Nature-Conservancy", "place_id": "ChIJIWZRKeHKQIYRXxta3wOMGGc", "address": "1725 Hwy 6, Houston, TX 77077, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.5705632, 29.7714443], "type": "Point"}, "properties": {"photos": [{"width": 3024, "height": 4032, "html_attributions": ["<a href=\"https://maps.google.com/maps/contrib/108143329814504597326/photos\">State from Jake farm</a>"], "photo_reference": "CoQBdwAAAHHGGbI2T4wJVaswxD80ykIFgbKxQI9qGHBrqCL21PU3r78lDGGfyvyRDFLAjD2-iDHjvFQQAzLVPMkgVKxyxCpfTMMxV4dm-iv5Y3wkEn9rY40VGel7xevVB3wPugMHp5PgnK41Z8OuMkLwfWVpWt65PewtLOe0EXexm2lXwRpaEhD8W-S5weExUbOLYJPRsLhDGhTFF7X0kbkv03rSbD_HMCgbNqEOKg"}], "types": ["park", "point_of_interest", "establishment"], "reference": "CmRSAAAA-GmM9cZALBzJ1PSTGATOyXsETQiYoS6TE-H2zNRLXdOmhype6Up5A1BDLM-qkBMQTh0Md5gF1GrNkLx-sFJq7VxOEtD4kh2aPSmiZzHyZ3gUpXtQBFLqC6nHHgC7_EYUEhC-fz7USOyEbOSCTtX1DeH2GhTxHho7zY05sVxTfrKcwrnCkStCyg", "name": "Houston Audubon Society", "rating": 5, "id": "050a5458d86bdd1cee7b09678bd6256d0a20a73e", "job_title": "The-Nature-Conservancy", "place_id": "ChIJlQOxwVDbQIYR2uX_TZl0TYc", "address": "440 Wilchester Blvd, Houston, TX 77079, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.56820189999999, 29.770778], "type": "Point"}, "properties": {"photos": [{"width": 1800, "height": 1200, "html_attributions": ["<a href=\"https://maps.google.com/maps/contrib/108765250995932379967/photos\">Audubon Docent Guild</a>"], "photo_reference": "CoQBdwAAAJ25DuWeV5vINRKfuTHOxNCFmIpSQPstpLSBILrBv1cpHYGDOrHn008v3OKf_sKCIbHJpI40_gcJ13dWndY_-8MDPb92vwe6yaKWDP5SGbtsM_rQRZyfPBnZhV84o9KHtkepH2lH_Z1GfTD1fG6nfjxvGau8UungVfBHzegyB2LeEhCuEfULtNYsteOe5Ib14mdwGhQBZQsG_XWg9kRsVv8UCsbXqi6XbA"}], "types": ["park", "point_of_interest", "establishment"], "reference": "CmRSAAAAHoZJGINwUVvQbn3Eya9bJYAa0-GbwRTWZ4oXT48nWFN_kGalB01lFfYoxfX8TOdAer6bJWUaS2rLbopub-NFZ8SEGoT_MtDdMXVys66LHoeR0IOZ3NnKJr_tcie5fAyfEhABlKrm7Jjpr-9hfMMvpSKNGhS5LfkhaDBEd46Q-O4mbv5DLWVHpQ", "name": "Audubon Docent Guild", "rating": 5, "id": "7ddd5daf76cc4979e2ba6b062322d1c77d5d1c07", "job_title": "The-Nature-Conservancy", "place_id": "ChIJI9XyNFHbQIYRtwHb8EtTpeU", "address": "440 Wilchester Blvd, Houston, TX 77079, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.44932349999999, 29.7803218], "type": "Point"}, "properties": {"photos": [], "types": ["point_of_interest", "establishment"], "reference": "CmRSAAAANRNJzQZzKC496fzncyL-IQLTx7pvjnBxPKFKk0_Tf_TpTrv8UT7q8qFwl1cW8rFd6Cjc-ZEdj1qzylsleHY-pGno4CmRu23Bo7SDWDnBu1i1PKpBfQvkMfMSoG7RhAwPEhD3FXY60oQi-62IOcc0PdOuGhR7WhFJoGfGAxI016v6CvURIHkqCA", "name": "Coastal Conservation Association-Tx", "rating": 3, "id": "7258b034e119f31e82320bca6e72781ee9f79d75", "job_title": "Edf-Trading-North-America-LLC", "place_id": "ChIJcekacM_GQIYRPzL13cgQrPk", "address": "6919 Portwest Dr #100, Houston, TX 77024, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.47039, 29.655454], "type": "Point"}, "properties": {"photos": [{"width": 5312, "height": 2988, "html_attributions": ["<a href=\"https://maps.google.com/maps/contrib/101184977609161362375/photos\">aug4</a>"], "photo_reference": "CoQBdwAAAHc2TLqTN-8Qb1tcml2qk617bIImcDv0eUQaIxeih9JYojKLjnkZRH7NlBSY_DtgzW70-SFzGpKefWrU1mUitYSRsaVTnJ9BuRoHhlezc6F-1SN9xxUxfJDaz4gqD6BEGv73zYaCtDXDVb4ypkTJqjHKpVKqkBqPK3dE3B_VsRLTEhDwwUZHFWIFE5WGfgfY9K85GhTOWaw1yIWoO4XAK1-kHJ8bHf7CQw"}], "types": ["park", "point_of_interest", "establishment"], "reference": "CmRRAAAAv84qau9ejslXruJ_BXgbYCg3ifLDSIT_ShHfdiVK0CRD06eBSKLunklQg1cgYa1VRj-pXcyv2OsXGuUFs-3hiXWdOrnKiOa06hoaA_idOq_k8F7FTy9YuK25dIw7oCtIEhBxCugCNdyEDbnlGjLd64h3GhQ13binnrOHug4dVLv-7E76Xof6pw", "name": "Willow Waterhole Greenspace", "rating": 4.3, "id": "0127506e8071350c2d48f0ca56e939045297a0f4", "job_title": "Edf-Trading-North-America-LLC", "place_id": "ChIJR6_2zTzqQIYRsA7wExgfDWs", "address": "S Willow Dr, Houston, TX 77035, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.4003322, 29.7388505], "type": "Point"}, "properties": {"photos": [{"width": 1136, "height": 640, "html_attributions": ["<a href=\"https://maps.google.com/maps/contrib/117056878997299689379/photos\">Marisol Brown</a>"], "photo_reference": "CoQBdwAAAPPaCV4ksk-XXl80Tl4Cge5A8tX-4jbFg-_sruzKMOJr9ZZoFyw3uEoM70qstYbrz8qFMEXQSwoBCmvBSb0XNKFMVHFaDXD7RKZh3vVXKtWjiVcxDz_R6wNg3Nipi-xJLakUHrFp1p-HKLeo0XSloz8aOQ8fjIpRTU9ZfpysDbk8EhDm7E2iiCg41IjJTa3HAfnOGhT3I5_Ht_nwjjwqHuE02C984_ff-Q"}], "types": ["point_of_interest", "establishment"], "reference": "CmRRAAAAXRRD7ye9BoBbseap7oiyQw24saZB7wT7a7iJJWNC9n00F2etwOfOzb5FglJQSXH_4sS8rllKtk66h3P5rthIYzd30ZuoCUiUY6Kzxi5B2cLkYj_uYerFGFuPoxEL_z_PEhB6fdsZldo4GQHovU6vZN3PGhTPY4fh5rgghU2TJ_kgZoJ-Twnm5Q", "name": "Masters Fine Art Conservation", "rating": 5, "id": "a462c2eef4e22ea319485ae7b84f3d20756cbdd1", "job_title": "Edf-Trading-North-America-LLC", "place_id": "ChIJp8u2bZvAQIYRbosnWz6cVmY", "address": "1612 W Alabama St, Houston, TX 77006, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.3876169, 29.794149], "type": "Point"}, "properties": {"photos": [], "types": ["art_gallery", "point_of_interest", "establishment"], "reference": "CmRRAAAA55LAqvyOZVpOzlsPbSikYyYMYzujqZd6oY3kCqxnlbeT-3JsqLVE-OpgLlm459BLA-qND7_8V16nXfH0Mxvr-Sw-TGMuN8qbgjM2qfCJapnSdiDNwIiDVxuRm12srW_3EhArTktMdejVS67FvmXCkskHGhRHf4YDRy7SQHzh_xjWyKhj7VyKSA", "name": "Whitten & Proctor Fine Art Conservation", "rating": "NA", "id": "883a8c5ef35ab28e1630235ad65a6b16506a67fa", "job_title": "Edf-Trading-North-America-LLC", "place_id": "ChIJ8YuXE6K4QIYRn1SF1hazFEw", "address": "1236 Studewood St, Houston, TX 77008, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.3858767, 29.7300997], "type": "Point"}, "properties": {"photos": [], "types": ["point_of_interest", "establishment"], "reference": "CmRSAAAAn9YluXwwBfL4DsX4HSDQmgPwrvgX7aJca17ba9db9Nv712X-PVZA4AZcohsf-LiIYiTaoQWL0pyzZA9OyNFTUj6XhkGxwi716a3Ij1L78JETOM7Tm_UB5rlierYEJ_jHEhChDaz73miyTmAeXI6Et7JLGhQjBIz5zgaisu7OgsNoyqKtLE1RVw", "name": "St Mark Fine Arts Conservation", "rating": 5, "id": "ea2d4bac6d74716b33f456dff3aae0cc0b43cca3", "job_title": "Edf-Trading-North-America-LLC", "place_id": "ChIJKbDEoXm_QIYRcRFBlp0dE8A", "address": "4901 Main St, Houston, TX 77002, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.483218, 29.7482286], "type": "Point"}, "properties": {"photos": [], "types": ["point_of_interest", "establishment"], "reference": "CmRRAAAA0UxKfUIZBBhWU1vGNCur3ecQskqwM9fnf3H-SzYMGag0t5TwVjVSFxLmf1VR3B0946HelDyrdfkBmEzAGLJkQyckUwxXtFI8LCFBvEt00yULBK8rP-cLM1ZRroN02kMwEhBHej9ZJEp8xhuG117VnQtmGhQ31Cj8MFq1uA3D4Qco-SeVpdy0-Q", "name": "The Nature Conservancy", "rating": "NA", "id": "90af6fb9fb926dde9f7103577cebc4150bbb1dec", "job_title": "Edf-Trading-North-America-LLC", "place_id": "ChIJq-m4EX3AQIYRJkn4Lhccp2E", "address": "1800 Augusta Dr #240, Houston, TX 77057, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.42318089999999, 29.7345943], "type": "Point"}, "properties": {"photos": [{"width": 750, "height": 437, "html_attributions": ["<a href=\"https://maps.google.com/maps/contrib/106788706324997826205/photos\">Erika</a>"], "photo_reference": "CoQBdwAAAIbi6RzlrG2V42v_2luOihr4U0yhE2ABj9Gccg4NXJJPr_gf4Du4tN-E7Pw9FJASrUa0yQMW-h28Om2D3sAIaDFc1MJ2S3_s1-bVXnM17zYU4t4zk2U7qSJU0L-mEUGkghg1SHxFBxgJyW4z1Wy94hwPv0oERl9haQTg1lbj9BfhEhATgKjBXhnI3TatoEofTp0-GhQ9fbfeS9ldYLpEKKYG38V4Lyq5Qw"}], "types": ["point_of_interest", "establishment"], "reference": "CmRRAAAAaBMoP9gBEYQBB-6lINoUIxxKRK0KyFOOnzBCtxzXPPtnGhwaWe8Kf9PKIm_BN6teDF-AVDY3MXXf20zbAZiIgQzCO_4wkmVVkvnsk4Mv6-6HaI1wlRLdyskscXdVkzJREhC8KNqefQwz7RoRCZOOjpWYGhRmrgTfzArYhPNIL7sNpO15DOHsCw", "name": "Student Conservation Association", "rating": "NA", "id": "1c5ea7722fc0d99e9f7dfca55f5d9078224d51d3", "job_title": "Edf-Trading-North-America-LLC", "place_id": "ChIJQcqBXfDAQIYRErawO-goGj4", "address": "2990 Richmond Ave Suite #400, Houston, TX 77098, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-96.038102, 30.055621], "type": "Point"}, "properties": {"photos": [{"width": 984, "height": 985, "html_attributions": ["<a href=\"https://maps.google.com/maps/contrib/110279808588468038448/photos\">Peckerwood Garden Conservation Foundation</a>"], "photo_reference": "CoQBdwAAANBGKCRftArFoUdSh2b5ngvUOTAiZT3opA_kcxpVOP43I2SI4EpQhMQ8WdawD8JtyTLOx7bC_8lm2Cu9SwTWShd25pVxlbAIz6sgKDAvwMWp6jMvqynco493rAN2oPjtlnICRS_i5tVU9QyNXuXV8qFJOFnftR9qeK5iVpURWYNaEhCwAWV_9asOAOOwxUPyvddPGhSofqY8OwW9mX1NDxsTeN36oXch9g"}], "types": ["park", "point_of_interest", "establishment"], "reference": "CmRRAAAAFkBzKtCefJA3IyGfJiU8Q7LHaMh-sPr8m48dCDrJAld7Ngo0jo6F9MCmWzDbCe6YEb98YfupiOAdHlnhv10OsgBOA9OU4QkXRHBaIGeJ7esazo7IlHauWO9JAGek55PIEhBp7BPA_4GNZcEUwSqjLOypGhRmtYoq-CXU9vmLFNdZxQCaWR-_JQ", "name": "Peckerwood Garden Conservation Foundation", "rating": "NA", "id": "e618a4c618cd67ce4f5fdc165f640220ab3b53b2", "job_title": "Edf-Trading-North-America-LLC", "place_id": "ChIJmUR7pvHKRoYRIIl0o73bPGE", "address": "20559 Fm 359 Rd, Pine Island, TX 77445, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.64386449999999, 29.7515036], "type": "Point"}, "properties": {"photos": [], "types": ["point_of_interest", "establishment"], "reference": "CmRRAAAATHuqZlPJqEuNkLtQKI3QU7RAF9PzdW9YG76BtrSso1v5LeBJvODHXPkgtYddMBIFaYvjDGiS_9RtY028Mog_k5_SqnU9p6948FLx1CqpWby2zHw_50hC5UjVTKtRrE3yEhBjyLXRgftI4ZagDDdDfgU2GhRysySnahd3Z3Nm55uxS9_EWsCzWw", "name": "H2O Conservation Technology", "rating": "NA", "id": "30c07988ef8dfc62dac712b9d587daa4a36f2539", "job_title": "Edf-Trading-North-America-LLC", "place_id": "ChIJIWZRKeHKQIYRXxta3wOMGGc", "address": "1725 Hwy 6, Houston, TX 77077, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.5705632, 29.7714443], "type": "Point"}, "properties": {"photos": [{"width": 3024, "height": 4032, "html_attributions": ["<a href=\"https://maps.google.com/maps/contrib/108143329814504597326/photos\">State from Jake farm</a>"], "photo_reference": "CoQBdwAAAOH_8vGDIbsAV03G62430Y5N3hatYlg8wn32hCMMLYXXeohMpJnJpk1QGb6qv_KgAHgJLX2ldbiuDCT9hNbjVwKV8IqDS3dAcrEc2uW_WZCLyvl6l_zOYvH0kVNt5veoZ4yZYsIObR3ibjtoZxMhIZCWJsmh2AQJC2UOqWbQtuY0EhB5UWrbBcIaNcLF4NsrmLVDGhSnjtSbUKKhp6661e0ztUGgpo_oPQ"}], "types": ["park", "point_of_interest", "establishment"], "reference": "CmRSAAAAT-SKbGd8eC0k-tK2VOnWqB_RdznLV2QNsw6ZqVVoQ5FMOD7Lvz9Ctc1BhudSh-c6-d3DVAZ3qZW6IJK_64YXfhpq5Lmy_7iUF5td6exRREJQObSBUBT1m4n4Y2QuHM5MEhA6uYL9ytHfmvr4mrQ1Rve3GhTnU556xbfSbKhkKD14RykXWni6fg", "name": "Houston Audubon Society", "rating": 5, "id": "050a5458d86bdd1cee7b09678bd6256d0a20a73e", "job_title": "Edf-Trading-North-America-LLC", "place_id": "ChIJlQOxwVDbQIYR2uX_TZl0TYc", "address": "440 Wilchester Blvd, Houston, TX 77079, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.56820189999999, 29.770778], "type": "Point"}, "properties": {"photos": [{"width": 1800, "height": 1200, "html_attributions": ["<a href=\"https://maps.google.com/maps/contrib/108765250995932379967/photos\">Audubon Docent Guild</a>"], "photo_reference": "CoQBdwAAAOfK72eRJfIrxOkpDR241Gcmn7DHbMP0ZGqRKKHNuJLPPjqUFCoO8aGswNIV3qilJz8krtW4k07rWJ4ImGVwyOSrkG0dyLbriS77xN_A6kz5PyUX2AHtUHTVUDFhmf9dSB07YoiPU5DxQxueNC1T5TOQ6cTgtzz_PYn3RB3I60xXEhD_59c_ux750Nh2QrIh9zh2GhQYh9rNF0RxjCXI-TS2JkwZsXeYug"}], "types": ["park", "point_of_interest", "establishment"], "reference": "CmRSAAAAU-BwEYblHE1vNdY-XYDEEeSCI2TFNa_wsLaOVRVD0Dgg0et0f36iuBQVSjctOh_WvrJ8mnG3-5iEhhnM7h71E-KG7p3_r8knT82_I7KeQxAQFQlFQ96b3DFhHfEFVFk1EhDIDTKdZnLMevj1KPf46_A7GhTcrkCG3-7gjANNEsqiMLIFvYfNzA", "name": "Audubon Docent Guild", "rating": 5, "id": "7ddd5daf76cc4979e2ba6b062322d1c77d5d1c07", "job_title": "Edf-Trading-North-America-LLC", "place_id": "ChIJI9XyNFHbQIYRtwHb8EtTpeU", "address": "440 Wilchester Blvd, Houston, TX 77079, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.44932349999999, 29.7803218], "type": "Point"}, "properties": {"photos": [], "types": ["point_of_interest", "establishment"], "reference": "CmRSAAAADnbVeRAcch6ccm9jM0doEDCvVUzpZgWXNHs7bFWc0EID9eePFDUBUiANmoON3FUVJvkLXaUF5mQsgvDraw8GiKOM-xjq86xHMBSW3jt8T9j7E84vEwds46c9jqHqN27iEhCozhfAFeZA-fjfNS0DFlpgGhROgfxPAsWy57W3BI_b_SMIFwowcg", "name": "Coastal Conservation Association-Tx", "rating": 3, "id": "7258b034e119f31e82320bca6e72781ee9f79d75", "job_title": "La-Quinta-Inns-%26-Suites", "place_id": "ChIJcekacM_GQIYRPzL13cgQrPk", "address": "6919 Portwest Dr #100, Houston, TX 77024, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.47039, 29.655454], "type": "Point"}, "properties": {"photos": [{"width": 5312, "height": 2988, "html_attributions": ["<a href=\"https://maps.google.com/maps/contrib/101184977609161362375/photos\">aug4</a>"], "photo_reference": "CoQBdwAAAC4RA8WXhu34bfbSAccajA7mMjwUXKcLhrga0wva2jE8JN6JuM5EhfeTFLvj5uw_7MIj4_iwABPmY-xR-mTwReDaUtLuw1VqbixDdLs8iUauVm8jSvN7laqByGDrkvhkl4v2PI6Z-Gk1lmUmdX_9DVXyge_7xxQ5sdqxbWfPsS0vEhAEiSZS-0KFevACdXMepuqRGhSGX4YfNl5R5slcxyfrnSQ8b1QJOA"}], "types": ["park", "point_of_interest", "establishment"], "reference": "CmRRAAAAmtjJlPnbkoA_wMNW_arU1NALpedVMV5oRHzihyvVSwkqvCBBQmtWMSDaBAfWsrh5Gtdxbj_N6C4YlGdAMZ2IBncWUn6NSI5xOswA0Dh4RLJRNzINdlCSDnibx25M2xJ7EhCvnuq7IoFGvWXNHD7UdS5lGhSsasoGhHGWVd7Pcmxab_AY48slnA", "name": "Willow Waterhole Greenspace", "rating": 4.3, "id": "0127506e8071350c2d48f0ca56e939045297a0f4", "job_title": "La-Quinta-Inns-%26-Suites", "place_id": "ChIJR6_2zTzqQIYRsA7wExgfDWs", "address": "S Willow Dr, Houston, TX 77035, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.4003322, 29.7388505], "type": "Point"}, "properties": {"photos": [{"width": 1136, "height": 640, "html_attributions": ["<a href=\"https://maps.google.com/maps/contrib/117056878997299689379/photos\">Marisol Brown</a>"], "photo_reference": "CoQBdwAAABU_hDP4ei9Dvvml5IrG8K15gJwsPDyvS-ZIki3Dh9RK0BqA9teybioCGiHE_dOd4lPAg814tTulv69ICXCrAFy9HuepMviapYVIe3VUSPrdcQYWKHhUFfO9CGsX82y5Wz9vXyfzURzNfrocwXwXCq903max-0FdF9HVNuuzw1mhEhB8eLrUQ5a9O-WEolf4NwiTGhTuhoTOWvG5N_722khB5cBchr-JMQ"}], "types": ["point_of_interest", "establishment"], "reference": "CmRRAAAAS9GDOVmtjPTcaichSDlIe2R4pgWY1vW6P8NyQoyKd8qk06kIt_1DDhsGFt8HpKQHL6VUqOtGAVOIUGaJijT-bzqACGRIMlQDv7FwJfxErDiO-tuYuH_1qQKrX831MJH6EhC8nZ6pC8aHmS8kPvpp62SLGhSHDTY3BLVdORt_Lfn9YZbxRvMVLA", "name": "Masters Fine Art Conservation", "rating": 5, "id": "a462c2eef4e22ea319485ae7b84f3d20756cbdd1", "job_title": "La-Quinta-Inns-%26-Suites", "place_id": "ChIJp8u2bZvAQIYRbosnWz6cVmY", "address": "1612 W Alabama St, Houston, TX 77006, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.3876169, 29.794149], "type": "Point"}, "properties": {"photos": [], "types": ["art_gallery", "point_of_interest", "establishment"], "reference": "CmRRAAAAK_auuqBscKsoB-GJLaGCofEAR_v_tq60C8BAqrbP4a4zLNXcJuHmL6AM-tVs5lxoJm1Syyh6DguHLMFwNu3MjK032Dbno8Vgbjr0BbXHxujolhmiCOG-PqC4pNA4-qsrEhBwyXa2o6X8vIiI-NjFKUB1GhQuB6VVrXITdv8SMaelW_m6X9BCog", "name": "Whitten & Proctor Fine Art Conservation", "rating": "NA", "id": "883a8c5ef35ab28e1630235ad65a6b16506a67fa", "job_title": "La-Quinta-Inns-%26-Suites", "place_id": "ChIJ8YuXE6K4QIYRn1SF1hazFEw", "address": "1236 Studewood St, Houston, TX 77008, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.3858767, 29.7300997], "type": "Point"}, "properties": {"photos": [], "types": ["point_of_interest", "establishment"], "reference": "CmRSAAAAK3MQrKt1asfhLK4kehgZSSCPgI2n8zUlbfO1tvKfq8VYMgVo3wOyQYusYL8CpikSU86qLC503BSh-CD1SIGESYDN_xW_qgSYV-Z6l58S-Ee6y3M1ajCjzYIIc4HSHxigEhCnH4Gpm0DWGsHykBytQR27GhQVLI2NGpCuAjYAHHZ-8Yd2ydjfVA", "name": "St Mark Fine Arts Conservation", "rating": 5, "id": "ea2d4bac6d74716b33f456dff3aae0cc0b43cca3", "job_title": "La-Quinta-Inns-%26-Suites", "place_id": "ChIJKbDEoXm_QIYRcRFBlp0dE8A", "address": "4901 Main St, Houston, TX 77002, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.483218, 29.7482286], "type": "Point"}, "properties": {"photos": [], "types": ["point_of_interest", "establishment"], "reference": "CmRRAAAAwNVXT0g_Wp7060PQNvWnJw55eO-IPuly2Vgeud8WGRMA_XuoTWyu48bb5bdMXwDcFpqRB-768yi9x1RdyNnEFTl-AgSEs8SkMC6Z_lirT4r38QQ-dxY6Gvf8oL8e_eDeEhCNGzuCHepa-BOQdOiqNUANGhQcZ8GFF8Ypa7RwuFpCuoB0x5D-mQ", "name": "The Nature Conservancy", "rating": "NA", "id": "90af6fb9fb926dde9f7103577cebc4150bbb1dec", "job_title": "La-Quinta-Inns-%26-Suites", "place_id": "ChIJq-m4EX3AQIYRJkn4Lhccp2E", "address": "1800 Augusta Dr #240, Houston, TX 77057, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.42318089999999, 29.7345943], "type": "Point"}, "properties": {"photos": [{"width": 750, "height": 437, "html_attributions": ["<a href=\"https://maps.google.com/maps/contrib/106788706324997826205/photos\">Erika</a>"], "photo_reference": "CoQBdwAAAGX0FgQLC_tWXNmPprnLWBkUDli_wggR9PWe6BzntOKUscx1y6ORh4xq_NJFaaY-0K8JuhnEnUyz1MojTjtD6s3ih8bbsi-vnFR-g46VmIOyShK9v2YTnNFie3jMfgJv8WVg7ZGnE5X5llHEVGe5om6rqR8dP8FTVef-1aPcG1CpEhBBz3oOLMEuaRXZNF4_HIJJGhSa1E7sWZvs3p1X_QkMwg6rq45Y3A"}], "types": ["point_of_interest", "establishment"], "reference": "CmRRAAAA978ZdVX4gknvo6igjXxiLsDbCZtF3j_2yoaricg8f0pWBpoDEvu1UbIvUPRJq025FPZCLeXoRB3X4E1TN-oPSLplX69OYCDQrcaxhrAF3o-KdislA4FPt8tyrnPtvyGQEhC4uarwpPI2rn5mGNOIz8tmGhRB_ztEjiEPX8NS6KeK8OBGoGfExg", "name": "Student Conservation Association", "rating": "NA", "id": "1c5ea7722fc0d99e9f7dfca55f5d9078224d51d3", "job_title": "La-Quinta-Inns-%26-Suites", "place_id": "ChIJQcqBXfDAQIYRErawO-goGj4", "address": "2990 Richmond Ave Suite #400, Houston, TX 77098, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-96.038102, 30.055621], "type": "Point"}, "properties": {"photos": [{"width": 984, "height": 985, "html_attributions": ["<a href=\"https://maps.google.com/maps/contrib/110279808588468038448/photos\">Peckerwood Garden Conservation Foundation</a>"], "photo_reference": "CoQBdwAAAOw7RSJUNKZ0KW7cffuTlLKDNX82JcQ2SrL-9sUCSzUJgD083Vu8Fsbqx5XeNiGlnpTivWVuVjVfX4C23y32a0PYja0OkAfknOgOqqCnNi6OOUhzo2aQuoaiz0M2kOhhmXy_qiTmKyLLSrcTlzTC-YPgG2MKAiaKdTtRaB1y6pEXEhCFrtqtvwxAfwPam0XmO2xBGhSd0jxOxEa8YBWEe4S9jzTAO0Yw1g"}], "types": ["park", "point_of_interest", "establishment"], "reference": "CmRRAAAA3dnwLHoxBsv_jVFY2VkZG_Y31UyN3g1STWTAaD-NNAwSWH8-ptZVGHrK_evhI5X4FCNrG1AJ1fESaqdEL5YrSGmTmyMUEYDfirTZPMTW-g1BVmEiNVP3_C3iAvP3lycpEhDgUOxk71SJo4IOTAXfgo1oGhRJBqoyILtWv2fVWpTU1VGFh2xxxw", "name": "Peckerwood Garden Conservation Foundation", "rating": "NA", "id": "e618a4c618cd67ce4f5fdc165f640220ab3b53b2", "job_title": "La-Quinta-Inns-%26-Suites", "place_id": "ChIJmUR7pvHKRoYRIIl0o73bPGE", "address": "20559 Fm 359 Rd, Pine Island, TX 77445, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.64386449999999, 29.7515036], "type": "Point"}, "properties": {"photos": [], "types": ["point_of_interest", "establishment"], "reference": "CmRRAAAANG2fi2RZIQeUcthTWp-5B5oG6FOF_CiMI8DiivwVUrCVoiDOehDmswIDwYPd6-p0Is5JmFsMr588bnIObcUiQDIiRF0v0JUhJOysD0e20Qh78T-pFiEI9DdV3QWMLcAEEhD-ga1GR-SA1iXMuyip9FoSGhQtC3RLFvTCL5c-YVN3-9sBU0a1Uw", "name": "H2O Conservation Technology", "rating": "NA", "id": "30c07988ef8dfc62dac712b9d587daa4a36f2539", "job_title": "La-Quinta-Inns-%26-Suites", "place_id": "ChIJIWZRKeHKQIYRXxta3wOMGGc", "address": "1725 Hwy 6, Houston, TX 77077, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.5705632, 29.7714443], "type": "Point"}, "properties": {"photos": [{"width": 3024, "height": 4032, "html_attributions": ["<a href=\"https://maps.google.com/maps/contrib/108143329814504597326/photos\">State from Jake farm</a>"], "photo_reference": "CoQBdwAAAC5jk48c4WSWBT_CMeSqKlpZqy87gpHH8CqZXixQDTqmCPXle7ksm7WYpkVAhSm1osuyaaL9y65Hs4aJF-we4Tpvlm6KafWfInpKwb4FXPllOeXtxvl80yfpDWrbx_ONxA1ysviADfUm1lOHihbnkWsysbylDEQOMh4PvqpPdKAXEhDCJPxxo6Di34j474FfUEEMGhQGjjDQz9gMAH8h99OyKIQGa9ZMCQ"}], "types": ["park", "point_of_interest", "establishment"], "reference": "CmRSAAAAVOiczHqam3-0yFdcknYhEPaH6TVsEJAIgpJ5S2W8F8-m4Kxq_iQ4xmfi5XFxFH1Q3jgDdGTgKuhSIx50P4VrrAlS7Z5gK4P1mKi0eMNPcRuzwO9z8hY53bffWKPvqB5dEhB1ZHdTLJ_fQoELpExYQg7eGhS5MJYGv0jZOGzNJHpe9jrwwiRnBg", "name": "Houston Audubon Society", "rating": 5, "id": "050a5458d86bdd1cee7b09678bd6256d0a20a73e", "job_title": "La-Quinta-Inns-%26-Suites", "place_id": "ChIJlQOxwVDbQIYR2uX_TZl0TYc", "address": "440 Wilchester Blvd, Houston, TX 77079, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.56820189999999, 29.770778], "type": "Point"}, "properties": {"photos": [{"width": 1800, "height": 1200, "html_attributions": ["<a href=\"https://maps.google.com/maps/contrib/108765250995932379967/photos\">Audubon Docent Guild</a>"], "photo_reference": "CoQBdwAAAJwsEKIlvlQfhPdcgAhbSnjMKlH8okI9Gvx88pVv4UGX9GZbSb89AclTNi4R4dt_RP-gTW8drJGkzmdLHvVY_Gd8ekZnJqNNZD8GQma-zn1zGGx3PGZ2gAqu0Hlac1NLwUK_o9XnYDE13hJnctapR2zApx50fJAzVDe2bmn-iT18EhAmrDoa3PNMwsvi9dGhWrayGhSmJc9nbEYe6hcG9JsZVK_Sb11O-A"}], "types": ["park", "point_of_interest", "establishment"], "reference": "CmRSAAAAUCmvLs11a6Hf75LXYF-a_WS0DLTpesUKPutL8VkHS4BaeLSAkk6TUDM_Oi35oDXN0pPhL-O9O_363UENbEvWCsRzJSJn99HTdxY6eYqt0c8G0fsXnhqIejVxEpJ6JXuSEhBx0O0fh-SezyLRYNjG68xZGhS8E2IBjcy1oYzgKa4U_o3t_DFChw", "name": "Audubon Docent Guild", "rating": 5, "id": "7ddd5daf76cc4979e2ba6b062322d1c77d5d1c07", "job_title": "La-Quinta-Inns-%26-Suites", "place_id": "ChIJI9XyNFHbQIYRtwHb8EtTpeU", "address": "440 Wilchester Blvd, Houston, TX 77079, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.44932349999999, 29.7803218], "type": "Point"}, "properties": {"photos": [], "types": ["point_of_interest", "establishment"], "reference": "CmRSAAAA3QUONNRX1b3vmc74FcCwCgNlgRH2IGH0cfZZnM9dw-rs_fBHbYI6_4RlGRO4yXAJchj8BHRIN9SzKEwfKcbXXljc2mzvO2wRfs5_klNk8UrqDMab8TIWab5LffSwqD3-EhBzLj1eiWDuX38g6bXJmSbBGhTEVuY5AsVOAJ5R1ew0j_pMx30t3Q", "name": "Coastal Conservation Association-Tx", "rating": 3, "id": "7258b034e119f31e82320bca6e72781ee9f79d75", "job_title": "Texas-Campaign-For-the-Environment", "place_id": "ChIJcekacM_GQIYRPzL13cgQrPk", "address": "6919 Portwest Dr #100, Houston, TX 77024, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.47039, 29.655454], "type": "Point"}, "properties": {"photos": [{"width": 5312, "height": 2988, "html_attributions": ["<a href=\"https://maps.google.com/maps/contrib/101184977609161362375/photos\">aug4</a>"], "photo_reference": "CoQBdwAAAPsswreqacd0NB7XR__bmAThtY5lnv0xaby_4lKYi8VQtUj2xNnoR7vJ_iv7P_Q-eLa9jd6ik_rf41YVyylEIiX6NMhNTZictR9EaO0xt7b-cmgBMgRx1Qh4IW379LTXT31kvQzywerD4X3WvgzwNPbICWtJ3jkSsAp6ArobTZSHEhDn1fKcNNshgyHGec9FE_2yGhSiJboMh0yPPI0NnB_vv3MDe3ha0A"}], "types": ["park", "point_of_interest", "establishment"], "reference": "CmRRAAAAwa1gkmkz2373EjTtuH2xgPa1CqDfUnLH9gvy8kxr-rWjEsdZxUwVyHEi7Y5iJeyiyLEbu5gfgDrxIhQG4dYp_D5fANHO4nZIz4dz1IMJL0bUjhODS3NTpKrvSGZObGz8EhCixWpfHkE6TIqvEjZbOSEFGhS2nOezc2LPT4LRu4SJrO16uWeZdQ", "name": "Willow Waterhole Greenspace", "rating": 4.3, "id": "0127506e8071350c2d48f0ca56e939045297a0f4", "job_title": "Texas-Campaign-For-the-Environment", "place_id": "ChIJR6_2zTzqQIYRsA7wExgfDWs", "address": "S Willow Dr, Houston, TX 77035, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.4003322, 29.7388505], "type": "Point"}, "properties": {"photos": [{"width": 1136, "height": 640, "html_attributions": ["<a href=\"https://maps.google.com/maps/contrib/117056878997299689379/photos\">Marisol Brown</a>"], "photo_reference": "CoQBdwAAAK-I94MgPY6rgilLMhQ-T-VQMd0aqZN5dxxXnl2rycyLqf1yT_weD0pmNc5ETfScSHYTR0bNkaeUNHzbBZ98D6CsgBLUvu5OQsKAZwjnVqUMTpQF9eizvjA86AJ4mn2x3pwdheo6geR13H5eW8XthUMldaAR_LixsXiaiml5HY3xEhDxh379MmMVp1e4jVJ_wIH5GhRxOqjr3PS4HUhND2T_PSPnOiKi2A"}], "types": ["point_of_interest", "establishment"], "reference": "CmRRAAAADVKG-SpqU1A2M_XiMAAIUTsbfUt2T3RFjYg5R6DV4ycaM21WGPWEf8-qXsQrmPsaVM0ciSYWeCufFB87q1IXq1dEJRmSxmEFmAr2dXltaXGh4FjZ7-jeeM5R8zxDfSRNEhCx6D9Sc12gGqiNY3D0UVafGhR2kARCF-gXvi8x9d1DjIOW45zGRg", "name": "Masters Fine Art Conservation", "rating": 5, "id": "a462c2eef4e22ea319485ae7b84f3d20756cbdd1", "job_title": "Texas-Campaign-For-the-Environment", "place_id": "ChIJp8u2bZvAQIYRbosnWz6cVmY", "address": "1612 W Alabama St, Houston, TX 77006, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.3876169, 29.794149], "type": "Point"}, "properties": {"photos": [], "types": ["art_gallery", "point_of_interest", "establishment"], "reference": "CmRRAAAA5cY4JsTnhZYAnorhtOp7K5GB1xsHeHYOUjd4VPMFFSLuJV3hpToghldPb9d-bd04HmpaFNxU-JTL1lmUZW_JjNCq2m3zbQ77M9Szr4xj8kRvV0f28mEY_HaEstlzs5ZMEhB-EjFsoinK5B1WRehSByNLGhS3_0QRtn5ORkRwGgAEuf1Iv-d0mw", "name": "Whitten & Proctor Fine Art Conservation", "rating": "NA", "id": "883a8c5ef35ab28e1630235ad65a6b16506a67fa", "job_title": "Texas-Campaign-For-the-Environment", "place_id": "ChIJ8YuXE6K4QIYRn1SF1hazFEw", "address": "1236 Studewood St, Houston, TX 77008, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.3858767, 29.7300997], "type": "Point"}, "properties": {"photos": [], "types": ["point_of_interest", "establishment"], "reference": "CmRSAAAAMrV3d9GbKR1JZ8d0POoeZVPBGN-N0YEt5VkHnHJA1kgWdpWRAhTNmTfGCZaGz4krVJZ49iIzmuIIBv08Q4H6wwiapwlm05vw1vb8lSwe9NqJ16c1eSEOHuiW77ZLdTRwEhCCBLdwSCoJq1wY4jTKNf2QGhT9vUA_xUe8uio1QQ7o49ULoEmlJA", "name": "St Mark Fine Arts Conservation", "rating": 5, "id": "ea2d4bac6d74716b33f456dff3aae0cc0b43cca3", "job_title": "Texas-Campaign-For-the-Environment", "place_id": "ChIJKbDEoXm_QIYRcRFBlp0dE8A", "address": "4901 Main St, Houston, TX 77002, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.483218, 29.7482286], "type": "Point"}, "properties": {"photos": [], "types": ["point_of_interest", "establishment"], "reference": "CmRRAAAAqOzfMknz4GoFe01DszSR7XPhqTmtBbc5ytreIW9XIfd3wAhh8O6fmuGQ-m72zyQwDHGr0f9GhQ2Xz0f3C-JypNAwelX4ZBQpHw--IJY3X_UDq7X4Bv_oaD5_KMUrAtCdEhA1mb6wdiRNjaddtqxvSW4BGhRyAKfLMGwrlv9lp_rhmuLzp8VpzA", "name": "The Nature Conservancy", "rating": "NA", "id": "90af6fb9fb926dde9f7103577cebc4150bbb1dec", "job_title": "Texas-Campaign-For-the-Environment", "place_id": "ChIJq-m4EX3AQIYRJkn4Lhccp2E", "address": "1800 Augusta Dr #240, Houston, TX 77057, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.42318089999999, 29.7345943], "type": "Point"}, "properties": {"photos": [{"width": 750, "height": 437, "html_attributions": ["<a href=\"https://maps.google.com/maps/contrib/106788706324997826205/photos\">Erika</a>"], "photo_reference": "CoQBdwAAANDauoXa8wUXxYGdOV0lxHeywjFzbBkL-LkWQ5sQgZNFxHdDLEAKBqt3SVskcHkPubm13-tXh1jjtvCylxzzajXZ3LN5uAomJl9Y28qSkIA_TDsVNq-zJETD7pcz_TPjCmL7-Zj_hWYoDYSlpKdOQBMTi9naYLSOGZ9vuObMpDDiEhDI2sUKwvJQRL-DaHByd3oEGhR1JXpAJS3SceLJG50xcrqbxX6Vtg"}], "types": ["point_of_interest", "establishment"], "reference": "CmRRAAAAMt8d0H-x246r200Xe5-e5NCTJjqdf4jfrKxPRwkKYhMgSDyUE5fQao_NRbfalRMyMUJbkiENBcnwdGYtw_Y2y-f0TzYb1ZTKN8VLMK35A5pH-mZ6yOQ7ocnblyfKETkIEhDKpmxJPayoebLmuBPmEZGbGhSWkwCm1SefvmDYcw77sCnGJ_L4-w", "name": "Student Conservation Association", "rating": "NA", "id": "1c5ea7722fc0d99e9f7dfca55f5d9078224d51d3", "job_title": "Texas-Campaign-For-the-Environment", "place_id": "ChIJQcqBXfDAQIYRErawO-goGj4", "address": "2990 Richmond Ave Suite #400, Houston, TX 77098, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-96.038102, 30.055621], "type": "Point"}, "properties": {"photos": [{"width": 984, "height": 985, "html_attributions": ["<a href=\"https://maps.google.com/maps/contrib/110279808588468038448/photos\">Peckerwood Garden Conservation Foundation</a>"], "photo_reference": "CoQBdwAAAG8MMPBuEw8Z-w-7hiJtZGyYNEFFvZGYltbhlAycKhLXrLKJHICG-kG2IPPcTDiqp3TGk0QItrVStLp5r5d70AOCLyZhbixZgqX4UCpdvpDF161Am5URhRzvdKRnnzmdoB6G1JbLqwThhTijqWunNIEktLgv_qrwLu3DNvnKT4WlEhABVIXqjE2-GoKYG3k1ncsBGhR2SZ6KcRVqT-rWUwMEl4mBFIQntA"}], "types": ["park", "point_of_interest", "establishment"], "reference": "CmRRAAAATI-z02bVgOw6K3KNkKlP5YQ726cGx89MN6Dqj9H68Sy2iHGJ1NJDjW_4OYcSZUxrHh3CoGCXAoC5TzOvEyJoik0nuUTnWeniNJp3KCqhLlLlEjlZxknp3LYUlQrVNgJ8EhDD_ftN8G8e7T9CN4XZZOrmGhSvpOtNUQRSgfNZUSm_4p2O6lZQFA", "name": "Peckerwood Garden Conservation Foundation", "rating": "NA", "id": "e618a4c618cd67ce4f5fdc165f640220ab3b53b2", "job_title": "Texas-Campaign-For-the-Environment", "place_id": "ChIJmUR7pvHKRoYRIIl0o73bPGE", "address": "20559 Fm 359 Rd, Pine Island, TX 77445, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.64386449999999, 29.7515036], "type": "Point"}, "properties": {"photos": [], "types": ["point_of_interest", "establishment"], "reference": "CmRRAAAALUQudJw8hzkwmIblwc1Xqe1tBZVC3h39ub10uWtFih9dYw9YxiLbjboA5LAkAet9OlYrtmvxdAedPuPD_VX0vULmzqzq0ggVYaevhozxDS2nHqQ73uGfXR9xNEVifN7XEhCQ00dnDA6-PZ86zKo6j9HmGhRlz8r9OohnJ00geuP4cNQP6Qzd0Q", "name": "H2O Conservation Technology", "rating": "NA", "id": "30c07988ef8dfc62dac712b9d587daa4a36f2539", "job_title": "Texas-Campaign-For-the-Environment", "place_id": "ChIJIWZRKeHKQIYRXxta3wOMGGc", "address": "1725 Hwy 6, Houston, TX 77077, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.5705632, 29.7714443], "type": "Point"}, "properties": {"photos": [{"width": 3024, "height": 4032, "html_attributions": ["<a href=\"https://maps.google.com/maps/contrib/108143329814504597326/photos\">State from Jake farm</a>"], "photo_reference": "CoQBdwAAAErfQ-DfpPQsljq1hPXGWokzmXsFD777MVhFKj5dM25iTCVqH_o5o8ZZ8lciqTz9b893ApQ-yqEE34boYWMiBZ5UsnSa0VRn_M05GpNl0llLEYQLlqlhYx0fk2lS8uVjBG6iKnZhw7Aie6CN2EXJmoKvYGAMkjPjExTCGwimnt6ZEhBdoQpvH6Reda_iwyJR8wxxGhSCrguF5MIq8ABODS_33tnYG01Blg"}], "types": ["park", "point_of_interest", "establishment"], "reference": "CmRSAAAAluqba9Hm8wPQW4q1XMYvilSW0UCHgW3Xx5emdvd-gSJl4Xj7IFXrxSrFkBINSNVcq4JdGuRGmiXCCzSmhhaSh2P6DlCFfIxufE46XRjRLMeJA9OE7H4jxFrJf2Wf9ilpEhDTl1FCZhHfBGzdMvAeZ3vIGhQs2VkAy7ZHX6EaPn6-DMpe3OCCmA", "name": "Houston Audubon Society", "rating": 5, "id": "050a5458d86bdd1cee7b09678bd6256d0a20a73e", "job_title": "Texas-Campaign-For-the-Environment", "place_id": "ChIJlQOxwVDbQIYR2uX_TZl0TYc", "address": "440 Wilchester Blvd, Houston, TX 77079, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.56820189999999, 29.770778], "type": "Point"}, "properties": {"photos": [{"width": 1800, "height": 1200, "html_attributions": ["<a href=\"https://maps.google.com/maps/contrib/108765250995932379967/photos\">Audubon Docent Guild</a>"], "photo_reference": "CoQBdwAAAOEYDods9XTx15MUQPb7keLogCHZAunkCg70U10_qtJgrPIHVDtknScKhen_VtLenrV4J6A-wwpL5cpAsWddF4B-NZvs27R6Vvr8zkROcU7YgKkSTYgGBLHWwUuidBFLbAroyyja4S2Hel3pbVokJYocAbbQb5spkkgvM-ov6a6DEhBgM4qrS-A_AieSvolr-n2wGhRH1Wm0rFoXUCvHYzsQoIhV9N0z-g"}], "types": ["park", "point_of_interest", "establishment"], "reference": "CmRSAAAAgtRzLxV2ZSq0dHkLY8zgbl7nlIxpvZJNTwoqj5nKUfX7g-UGAhLuf6PtMBT13WzoQ7IAaH1vuBSWttrktQnAIs45POsNEi_ZEl5o_kuOag0fiX_GSRuWAhhPctl9J1h2EhDr-djs02YyUMoPeVPPLpS-GhTWj7oPirGFQ22xA_Jd_tELX_BuBQ", "name": "Audubon Docent Guild", "rating": 5, "id": "7ddd5daf76cc4979e2ba6b062322d1c77d5d1c07", "job_title": "Texas-Campaign-For-the-Environment", "place_id": "ChIJI9XyNFHbQIYRtwHb8EtTpeU", "address": "440 Wilchester Blvd, Houston, TX 77079, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.44932349999999, 29.7803218], "type": "Point"}, "properties": {"photos": [], "types": ["point_of_interest", "establishment"], "reference": "CmRSAAAAdQwJf96KmdAQQI9oQsIfnLf-JXUme3T63uGPPm2_VB8J42fc0R1seZAe1nhttqFzT4ACwnmxqaktSy-EWc9n-YdHUquEOEvgBgCIg0TepHj_hHvP0EvXyYye0jb0ezvHEhCGnQ6neN30a-znG-GXHqmuGhSl4CqS_mNZSID8ZVr-IxavtpaQ_A", "name": "Coastal Conservation Association-Tx", "rating": 3, "id": "7258b034e119f31e82320bca6e72781ee9f79d75", "job_title": "Rainbow-Personnel", "place_id": "ChIJcekacM_GQIYRPzL13cgQrPk", "address": "6919 Portwest Dr #100, Houston, TX 77024, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.47039, 29.655454], "type": "Point"}, "properties": {"photos": [{"width": 5312, "height": 2988, "html_attributions": ["<a href=\"https://maps.google.com/maps/contrib/101184977609161362375/photos\">aug4</a>"], "photo_reference": "CoQBdwAAAIvo2L0jt1S6vsjt6GyaEvNj8TfsD_tZ__JBrpNcaJGwkp2VRZZPdPtWP-8ht41d0vHAbf0mB9rj0nojg5FsSxu2DLPFLMiqGez9r0twZSQ6bXmHEprFZTY5ITMlh8GvoWc4OQ49cy6ol0iIT0EVVQ5ICtQ6Kik-B0bskqTFRkrWEhDroGfQO4jM_630RJdliMG1GhQLuuQSKFt3gfz8eiunb8OqkEj7LQ"}], "types": ["park", "point_of_interest", "establishment"], "reference": "CmRRAAAAiFJhvmLq3wa84IgLC0xoN-F-c7wKxXE7KXqwO3Drl6ifjS5PInP9VIBfS64L5_SduVnfL3EurOzr4eHeLTZbpO0Z9X8B27AG9GOZkMd8MzYjAqqEE3hUaw7j5OZZ_CqLEhCfGaWCrT8TKN4DDcsj-kEOGhQ2V5QvJl6ObSvjiQNlVVsK_su0xQ", "name": "Willow Waterhole Greenspace", "rating": 4.3, "id": "0127506e8071350c2d48f0ca56e939045297a0f4", "job_title": "Rainbow-Personnel", "place_id": "ChIJR6_2zTzqQIYRsA7wExgfDWs", "address": "S Willow Dr, Houston, TX 77035, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.4003322, 29.7388505], "type": "Point"}, "properties": {"photos": [{"width": 1136, "height": 640, "html_attributions": ["<a href=\"https://maps.google.com/maps/contrib/117056878997299689379/photos\">Marisol Brown</a>"], "photo_reference": "CoQBdwAAAMnp7Mb86gvAlPMzHQhuEdbh_g0-BdjYd94vBmwjCLaMnKd9lYognHaEh4cIy9JjXATiWM_ld6rLuhkHorcLAB9-3jG6NgPLIyao5JrqGkoEMDFB6FqBS15iRu3f-4gHaoYFTDlfalDKcSs1jQQJhe2upNmDpkHutyvYaYqceHdpEhDbX6VkCSIoZ4JReYokgrJNGhRbmkfC5T3AXqQHzP3vouGgl70LBw"}], "types": ["point_of_interest", "establishment"], "reference": "CmRRAAAA_fMLSVWYzkVxWGDj1lx3x99fdY2QuMWiEkUVHzv06Wq9JpYTqGEtCwkskLIcgB6-80iLK64RDDn27WMtLBSn-3AzHSY6Kpc52A2C9iLAwfJzzPzVTfDvsQJ0hyLGqBA5EhChqCFmkcN4Meg3hcEq07bWGhRA3JmyZQW-a0u3qCTGHXceoATt0Q", "name": "Masters Fine Art Conservation", "rating": 5, "id": "a462c2eef4e22ea319485ae7b84f3d20756cbdd1", "job_title": "Rainbow-Personnel", "place_id": "ChIJp8u2bZvAQIYRbosnWz6cVmY", "address": "1612 W Alabama St, Houston, TX 77006, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.3876169, 29.794149], "type": "Point"}, "properties": {"photos": [], "types": ["art_gallery", "point_of_interest", "establishment"], "reference": "CmRRAAAAz0Jw5jIqhm8mNJqpknWeF9DziO5zeeWQ5hE4kuDq9eyrT3LLWi-gOcWzCgo9gZkBY_atTNW3tmanUXrkOpPVi5nP6WEnCDAiAbejJ6Z-hjcXE9sPl2m5mAv2IMRNEq98EhD78g76TLpYVW2yKuUrPxthGhR9oLJ7UAsWNSJJ3MbUUBwuk5fk3w", "name": "Whitten & Proctor Fine Art Conservation", "rating": "NA", "id": "883a8c5ef35ab28e1630235ad65a6b16506a67fa", "job_title": "Rainbow-Personnel", "place_id": "ChIJ8YuXE6K4QIYRn1SF1hazFEw", "address": "1236 Studewood St, Houston, TX 77008, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.3858767, 29.7300997], "type": "Point"}, "properties": {"photos": [], "types": ["point_of_interest", "establishment"], "reference": "CmRSAAAA3F9taa4tPRGfxXMqTWjFpfrYFRgOwicbNAOAzygh8RAU_NkFBq6pGP69Nr1pptV7hCJpcsOeUIybJsHPL2Kpp7bUXGNeex4131DSmLVo895TY3H_Ns0ywDmXLmNjAxOMEhA6tuLY5DcLaRECKoprRe09GhTY8NOl9a6qSq_OV9lx1kr2Qi62KA", "name": "St Mark Fine Arts Conservation", "rating": 5, "id": "ea2d4bac6d74716b33f456dff3aae0cc0b43cca3", "job_title": "Rainbow-Personnel", "place_id": "ChIJKbDEoXm_QIYRcRFBlp0dE8A", "address": "4901 Main St, Houston, TX 77002, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.483218, 29.7482286], "type": "Point"}, "properties": {"photos": [], "types": ["point_of_interest", "establishment"], "reference": "CmRRAAAAM81vIIr6-F6MGZPhGW3FIzQmZ_ith0wMzJ4AQ6lH5zg8y6ERmBRxSzysD9Mc1eRpGK0qFOgiBdikMBLLxbC0rieveg1lfj8iMC2NABULVK1N0JUOurOcPbYxDaFs-2nwEhCeyY1P_qHULs1G2TXPwX1RGhQIbod789TuB5dwA6aepciYjRNQDQ", "name": "The Nature Conservancy", "rating": "NA", "id": "90af6fb9fb926dde9f7103577cebc4150bbb1dec", "job_title": "Rainbow-Personnel", "place_id": "ChIJq-m4EX3AQIYRJkn4Lhccp2E", "address": "1800 Augusta Dr #240, Houston, TX 77057, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.42318089999999, 29.7345943], "type": "Point"}, "properties": {"photos": [{"width": 750, "height": 437, "html_attributions": ["<a href=\"https://maps.google.com/maps/contrib/106788706324997826205/photos\">Erika</a>"], "photo_reference": "CoQBdwAAAP1k2ByL0EE7ydaEtjajxgDyqKJnNVl-vn-tEUdNfT6jKjApN8Wdft4ESODXG9HnQzHIzTE6-OZ_pwforIZYeBXOI6NF-bZVl6xKRht1GF6ONXbjfTFg260GRcuOSi0Ohg03otC6KIrC4136CUY2IKWoGnLTrNw66eP5TorUZLuDEhDOfcAKNVSvHBLx2I3L56YAGhQJ9B7M-2mYqt-Pa3kguMAc6NStcQ"}], "types": ["point_of_interest", "establishment"], "reference": "CmRRAAAAUk_42_scm9HAk52nj2CXkrnZ6H2RHV1aPTmbPgUyAVc5D5bvzCiIcxzERo6M0kArZn2u8omsaZtXeIOP75AkW53zRiGE7gVgtCn_ehOFXqyhb71j_uhK3_Sbvx-NShx7EhC8WsPeiSiHJTJ6cL8WYcd2GhS-yDlyvbpCVybvzGK6YnHnVAmhYQ", "name": "Student Conservation Association", "rating": "NA", "id": "1c5ea7722fc0d99e9f7dfca55f5d9078224d51d3", "job_title": "Rainbow-Personnel", "place_id": "ChIJQcqBXfDAQIYRErawO-goGj4", "address": "2990 Richmond Ave Suite #400, Houston, TX 77098, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-96.038102, 30.055621], "type": "Point"}, "properties": {"photos": [{"width": 984, "height": 985, "html_attributions": ["<a href=\"https://maps.google.com/maps/contrib/110279808588468038448/photos\">Peckerwood Garden Conservation Foundation</a>"], "photo_reference": "CoQBdwAAAIjn-Mv02-kD3UsvCVtdCGoobU0WIjykQK2z48kf20sd8B4XpFFwtIM9PBk3abQRMlcfAHBNKrGGa1RRoDEzKGSvz5ale4opFl-3MbkD0smvSA5OXOLVEUM69lT_hHz7ZXv3TX-pIOPOv0vGt4jxKNWvr-Fo_jpu_AAccm29AriTEhBHcfmaHr1YViIjZSuPSH-1GhRno_UtuPFPQCeen3LYPFOoKoDKjg"}], "types": ["park", "point_of_interest", "establishment"], "reference": "CmRRAAAAqNa0Plza_ia8kNFJftQa6sISAPYQSUhzpBYyFRl1BWr5uJtQEFbBc9GA_hdsWgHN-qwE3IzNckgGGQoHBGvSkQrNfseBXB8ZpkL-bPRSv623GhTxl29qM8GQkiu20H69EhAw7Fw1a5Z8M5I7kVGwdd3sGhQbInP1mGgV4dVuyC9xrW9zfqv2WA", "name": "Peckerwood Garden Conservation Foundation", "rating": "NA", "id": "e618a4c618cd67ce4f5fdc165f640220ab3b53b2", "job_title": "Rainbow-Personnel", "place_id": "ChIJmUR7pvHKRoYRIIl0o73bPGE", "address": "20559 Fm 359 Rd, Pine Island, TX 77445, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.64386449999999, 29.7515036], "type": "Point"}, "properties": {"photos": [], "types": ["point_of_interest", "establishment"], "reference": "CmRRAAAAMcWwY03wvJRuaFPtVTO9TM5t3Av3TknzI-3vs3RFpmzrdB8-SceZ_Dbc6WQreAwZxGYq-XwaZUq0bnFNjDbPOzq5ElRD0wKm_92TOWo5jpS63rP0YIz5RSz4ByIir17GEhBvJxKJdgwS_9G85VSjbgQ7GhTiBOGC1S_OjfFqOtmosPWAfFh9aA", "name": "H2O Conservation Technology", "rating": "NA", "id": "30c07988ef8dfc62dac712b9d587daa4a36f2539", "job_title": "Rainbow-Personnel", "place_id": "ChIJIWZRKeHKQIYRXxta3wOMGGc", "address": "1725 Hwy 6, Houston, TX 77077, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.5705632, 29.7714443], "type": "Point"}, "properties": {"photos": [{"width": 3024, "height": 4032, "html_attributions": ["<a href=\"https://maps.google.com/maps/contrib/108143329814504597326/photos\">State from Jake farm</a>"], "photo_reference": "CoQBdwAAADtpcc0j4KyhtUQ1_CKUn2sJufz8UJfp8jHWdfX0DCj8JsI7LiyppjnhC4lL1xUAm08dPaz5Har7qr1EztMDcBkYPMsNv2Bk2TBk35H9e2RBMQC8VUuPboWGe0hmOWV6qyJZ_sbwwLEmjHfvOmIPfxCxUiw9dVpOGUiGx3Iq6-ExEhD_pw6HDo8TwXYyRPWj0ldTGhQYGgdYzmp_RTqhPn5gChgq91lWPg"}], "types": ["park", "point_of_interest", "establishment"], "reference": "CmRSAAAAjYTH_x1nuEoXY3ZGQpHhIguRrLsQ6eSGf8sTLtYH1wHD6cEMAghduuxpuHJdvHOC_b3Im-Pof4rKowD8M1EYM9HUVlZ-iZx4tNVW0XPSLNX3HOzRKvrznJA6toUpF6z1EhBjpzblQSatlcL9g7xhiCJHGhQDi7C2_MMH1t6Rvbbx1nFhhqSoIA", "name": "Houston Audubon Society", "rating": 5, "id": "050a5458d86bdd1cee7b09678bd6256d0a20a73e", "job_title": "Rainbow-Personnel", "place_id": "ChIJlQOxwVDbQIYR2uX_TZl0TYc", "address": "440 Wilchester Blvd, Houston, TX 77079, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.56820189999999, 29.770778], "type": "Point"}, "properties": {"photos": [{"width": 1800, "height": 1200, "html_attributions": ["<a href=\"https://maps.google.com/maps/contrib/108765250995932379967/photos\">Audubon Docent Guild</a>"], "photo_reference": "CoQBdwAAADgrx0LEpX8X2HbTU_xnM9AhoFu4dl1uHRZESM0xCLyDRuZO70YsHV4tuNmn_clbmnUut97R5HpjwwxEUFnZTUqOObj1GujGIrtQqe6UxF_UWV14MEbu4tUOoODOX74JV6GPkwbdoo0z8z__yDp7mW16OgIMOjfhiQ-AKO1m0Jx3EhBJQBxrsc0YWT3WIKDQKVu_GhTcSqAKoOdeA7Q_WpZxK4HsElwESw"}], "types": ["park", "point_of_interest", "establishment"], "reference": "CmRSAAAARFhzzmnX3hfwZHCdwp_UVOswcokMxQO_luJm6Ybt8lvBzY9lptwV1Wn7xgawX5J4Eh8BsDRiMKI9K0DAzqftMlBtx-SE0ckjpx69TY6XPUgQ3fdYc-knl_7BBDS5w40LEhDXLaPDm00rDkiLJquTMJraGhQX37cvBz1eMmm1365UxsJWITDbGw", "name": "Audubon Docent Guild", "rating": 5, "id": "7ddd5daf76cc4979e2ba6b062322d1c77d5d1c07", "job_title": "Rainbow-Personnel", "place_id": "ChIJI9XyNFHbQIYRtwHb8EtTpeU", "address": "440 Wilchester Blvd, Houston, TX 77079, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.44932349999999, 29.7803218], "type": "Point"}, "properties": {"photos": [], "types": ["point_of_interest", "establishment"], "reference": "CmRSAAAA7MFPmX3qizUUVfTwA9PRWQn8-RndBWZG3nobWQH34vr7zl8Mo4how4dxb0k52R81P0Y0RZzlBQX-IwT99uXee0swptBcKZppiFg59c9J07UOXma1pqiymiqgFOGI9i0pEhBA46TlHXLhfU1Mm7TeBWoBGhSq3xxjOkYQJFItnw8oSXOjhs3uPg", "name": "Coastal Conservation Association-Tx", "rating": 3, "id": "7258b034e119f31e82320bca6e72781ee9f79d75", "job_title": "Acorn-International%2C-LLC-1", "place_id": "ChIJcekacM_GQIYRPzL13cgQrPk", "address": "6919 Portwest Dr #100, Houston, TX 77024, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.47039, 29.655454], "type": "Point"}, "properties": {"photos": [{"width": 5312, "height": 2988, "html_attributions": ["<a href=\"https://maps.google.com/maps/contrib/101184977609161362375/photos\">aug4</a>"], "photo_reference": "CoQBdwAAAC6Z5qqIW7i4pGV6D0bJIT--8wMlnglO9dUbSH0ySjPoiU3_fjpKbxAdhp6EnxyAjPc2zCx1FwAPUofjf82C9850hFi9byJma4e3Nmw-uOIPgtmAPo_rVwwHVc6uUsrT44ZrlVH4R_6WVKXfEUt2_Wz6xKEwMnSU17iPNrIoOICVEhB1mpxGKCjK3sTivY4hWTWdGhS6n0OAyTZOjIYLBiBmQnxC4GGxJQ"}], "types": ["park", "point_of_interest", "establishment"], "reference": "CmRRAAAA91OnskWPhX6dCIcO0oXGrPk6nu2Mnv-2_wTO-GSeJCz7CoRTEAeM6sM1XEf5ub_b3FO1VepgO-BLJy6_ukEaB71NA6sbxMN9V_tCAveDqLpO8tJJ8QHH6ZcdFbc9G7AqEhDgumYuieOJubYEtjXPE7qrGhQp8BV5kh5vvHXZzQlA9YSyTPCr-Q", "name": "Willow Waterhole Greenspace", "rating": 4.3, "id": "0127506e8071350c2d48f0ca56e939045297a0f4", "job_title": "Acorn-International%2C-LLC-1", "place_id": "ChIJR6_2zTzqQIYRsA7wExgfDWs", "address": "S Willow Dr, Houston, TX 77035, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.4003322, 29.7388505], "type": "Point"}, "properties": {"photos": [{"width": 1136, "height": 640, "html_attributions": ["<a href=\"https://maps.google.com/maps/contrib/117056878997299689379/photos\">Marisol Brown</a>"], "photo_reference": "CoQBdwAAACtEBuEeOzWNdOZj3Qj2NfqpeJt2uGWaq_s0gHeCiEs0tF_RvEzKxuk1E-DqM_B-iSnyTCnlY1FwAShuEA8hbbKugmwP1BIeJQARg7LAYWxk_FiFqf2a8S7FRKhoINoCuiMOrI3VxOBzTm7osSJ7LHLzA_1u2LuHS3nb1V4htchYEhAgbrrl9yirWyVrhtCBTgd9GhTdJrtzKMQzI5UqogjkqpCsMZ3-8Q"}], "types": ["point_of_interest", "establishment"], "reference": "CmRRAAAA8Yd96ZgKys-_Ce3RO4npsABwUF1_uLfzcPGakkCKetXa6bISBm731j95mx2K7_ASYJgtcQ-hAWAAzNGmJLCHneiwxTAAOTss8zA4i1-FYHEtC9bWfxX2xXgF5fHBJPnCEhDr-fTqBIlz1aYQ7pkxFZP2GhTgv0aNv929sB1LSHGqIrMnPhq0NQ", "name": "Masters Fine Art Conservation", "rating": 5, "id": "a462c2eef4e22ea319485ae7b84f3d20756cbdd1", "job_title": "Acorn-International%2C-LLC-1", "place_id": "ChIJp8u2bZvAQIYRbosnWz6cVmY", "address": "1612 W Alabama St, Houston, TX 77006, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.3876169, 29.794149], "type": "Point"}, "properties": {"photos": [], "types": ["art_gallery", "point_of_interest", "establishment"], "reference": "CmRRAAAA_ZYtbn0M_QKkYm0LH2BAWUMTRV5LQn9Ff65ynwQ_AX7t6bdrQJhRIvWbgci0LQyhbRjeFg6qdKgQu7cF3ogoYTcXMbOka9TkrMYg7_K7_eTO04tAfRXAfYpqK5XSCDf4EhDP_WpCDb_UOvekJkRHf7z3GhScCGphaBkxHDfjDQ0PL4oSk17ffg", "name": "Whitten & Proctor Fine Art Conservation", "rating": "NA", "id": "883a8c5ef35ab28e1630235ad65a6b16506a67fa", "job_title": "Acorn-International%2C-LLC-1", "place_id": "ChIJ8YuXE6K4QIYRn1SF1hazFEw", "address": "1236 Studewood St, Houston, TX 77008, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.3858767, 29.7300997], "type": "Point"}, "properties": {"photos": [], "types": ["point_of_interest", "establishment"], "reference": "CmRSAAAATjElCn7OA_HNzvGfxU4cSD5d6irRiVNvcBmSahqrFoP3pTc7stpCA9pktyd6TO-lp20wKLaHzm0uXqp3JApiX-HBfkzthjli4YJ57u-s_YYPEolIOWnKJq7z23lWylVCEhBT_KxAVZBrWjRIUQpR42xvGhQWLzAvdmnbs6vJGdYUuSkj07YfBw", "name": "St Mark Fine Arts Conservation", "rating": 5, "id": "ea2d4bac6d74716b33f456dff3aae0cc0b43cca3", "job_title": "Acorn-International%2C-LLC-1", "place_id": "ChIJKbDEoXm_QIYRcRFBlp0dE8A", "address": "4901 Main St, Houston, TX 77002, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.483218, 29.7482286], "type": "Point"}, "properties": {"photos": [], "types": ["point_of_interest", "establishment"], "reference": "CmRRAAAALAOVhaavDw33s8y8FM1RsRLzbVpJ0tLNVucDKgIwGH99y_6e9s-6UaZL_KzBG-zrp9sApYOEmIfHLpSfn36P0SKRrFUVHStuwde93_yDuwCd_eySzoLf1tUteA56eT-aEhA96dsP_JAM5r2L1Xr1_coTGhQhWmZP5rBkJcQziPlYLyum3jvcow", "name": "The Nature Conservancy", "rating": "NA", "id": "90af6fb9fb926dde9f7103577cebc4150bbb1dec", "job_title": "Acorn-International%2C-LLC-1", "place_id": "ChIJq-m4EX3AQIYRJkn4Lhccp2E", "address": "1800 Augusta Dr #240, Houston, TX 77057, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.42318089999999, 29.7345943], "type": "Point"}, "properties": {"photos": [{"width": 750, "height": 437, "html_attributions": ["<a href=\"https://maps.google.com/maps/contrib/106788706324997826205/photos\">Erika</a>"], "photo_reference": "CoQBdwAAADB_iB5WOnmCQs4yMnzV9_m-BOOj-wMo_RNF5vM32tfoXSJHpH82ZmqfQkJPRduSilE8mpz_WhjbzaSbyzpt3mi8YYwfpd9L2hlWMQ4yTkUwZwyj_g4xZnHNzo4StSSc1856chdE2hUHbQOFL9IUvZzYn6XAocgBWi1XfidR09ZJEhB1LuJ7nVR6_tA0YELaJdr9GhQ_QnUVmwsvn5UJP2PVN0RSiJQKqA"}], "types": ["point_of_interest", "establishment"], "reference": "CmRRAAAAOcLhT3UcUFEc3bg7Ll_N09htpeMhYQ0NVR-bHGLHCZozwtlbTMM8Pm1rEtS6g3KYeULQ02VOruzcn9XIchPmfN5NPF0Rs8GcV7MSGGiTcHd6RdZ_xtwlk_DRaowDI9IaEhDl6PjQPC5YoKuOITtKU5ILGhR-FTBn0ecGN-gBDaN24ZBoE8i7aQ", "name": "Student Conservation Association", "rating": "NA", "id": "1c5ea7722fc0d99e9f7dfca55f5d9078224d51d3", "job_title": "Acorn-International%2C-LLC-1", "place_id": "ChIJQcqBXfDAQIYRErawO-goGj4", "address": "2990 Richmond Ave Suite #400, Houston, TX 77098, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-96.038102, 30.055621], "type": "Point"}, "properties": {"photos": [{"width": 984, "height": 985, "html_attributions": ["<a href=\"https://maps.google.com/maps/contrib/110279808588468038448/photos\">Peckerwood Garden Conservation Foundation</a>"], "photo_reference": "CoQBdwAAAEmyY8IEkirnmcjoPpTQ4dKXrCv0FtTC-opgTWNFApNYdZKcF_FutuisscjBJW6U2KI2k8K1o8_jgYDZGShnB479Gvp7RLjYzp58NSWLY9CE7wUnjGIqGh-ss6GzQWVX7f_bReNm96OCdagCKsYSGuFmeTGkAQw4LzOww8jjAgytEhCR92zjtETh0ReIr844QW4FGhS9QspUulaAn3CM2N_suHTL5mAnDA"}], "types": ["park", "point_of_interest", "establishment"], "reference": "CmRRAAAALORZfozRuvtcsgeGVTZITx1ahrp3Co0KrCZBoGn0H-vV61Ky59dAM1AwGGmnXZiyGsTLzxLC88O_La6fNJSFM7xQOfhNA4LtAvMargnLjDixXIv0sqD62YEw_WgZKHNNEhC04MK2cWRYwJQiiGr9fsj-GhR4evmBaN4D7UkiFKL_It99Jj1_pA", "name": "Peckerwood Garden Conservation Foundation", "rating": "NA", "id": "e618a4c618cd67ce4f5fdc165f640220ab3b53b2", "job_title": "Acorn-International%2C-LLC-1", "place_id": "ChIJmUR7pvHKRoYRIIl0o73bPGE", "address": "20559 Fm 359 Rd, Pine Island, TX 77445, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.64386449999999, 29.7515036], "type": "Point"}, "properties": {"photos": [], "types": ["point_of_interest", "establishment"], "reference": "CmRRAAAAR1fX7oTF3lcJS5HkWFauFJYJJawqP96eOjj2NlMeuEnDxs5OkDuN2qX5JYH55v63Em1S4hBtWQDdCUy7wRU4pq6l8XIbujXAX26RjBno0DXUZGFat6PAXovw1lmaW67OEhArIx238_CaEbMSl0vGlYyvGhQnPV4g2wTWCwl_jWW3NZrCWd8Dwg", "name": "H2O Conservation Technology", "rating": "NA", "id": "30c07988ef8dfc62dac712b9d587daa4a36f2539", "job_title": "Acorn-International%2C-LLC-1", "place_id": "ChIJIWZRKeHKQIYRXxta3wOMGGc", "address": "1725 Hwy 6, Houston, TX 77077, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.5705632, 29.7714443], "type": "Point"}, "properties": {"photos": [{"width": 3024, "height": 4032, "html_attributions": ["<a href=\"https://maps.google.com/maps/contrib/108143329814504597326/photos\">State from Jake farm</a>"], "photo_reference": "CoQBdwAAANc-p4SpKRrqTH38aYAOed93j-7biEuLtdjcONwXC56L9LyJntJLvfokFWvDYUII9u2cMNx1n4Zpmj39ONCKuX7IqvuL6XiySKJHzX-91d9f6Ly6awMvw3cM3WhYZP-41X7XGR47ncBwkQHD4X1ZIyj1-uOpgvg_IcT3qlkojkGcEhD5rjsqTqUgmeFQjNuWkF0GGhRwDCwFrcqMmSQwtsJpFeiksXBHmA"}], "types": ["park", "point_of_interest", "establishment"], "reference": "CmRSAAAA8sYFezbB42sYx-pRBpNWioUizCVUWqJxQzKRS0AcV4t5e9aQ7eaUOwDLaXuz6NKXynAYagxmqVqNygB096IgVdsjIz-kfUl5c89TbNeBTDtpOvmeNzHDAzdrvrnCxk8zEhB-NtN8OfhXSbp2vhw9NfleGhSM-_k0ZiMlT-Iq3xI5yh_A3MMQiQ", "name": "Houston Audubon Society", "rating": 5, "id": "050a5458d86bdd1cee7b09678bd6256d0a20a73e", "job_title": "Acorn-International%2C-LLC-1", "place_id": "ChIJlQOxwVDbQIYR2uX_TZl0TYc", "address": "440 Wilchester Blvd, Houston, TX 77079, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.56820189999999, 29.770778], "type": "Point"}, "properties": {"photos": [{"width": 1800, "height": 1200, "html_attributions": ["<a href=\"https://maps.google.com/maps/contrib/108765250995932379967/photos\">Audubon Docent Guild</a>"], "photo_reference": "CoQBdwAAACQT9Q5E9NvksOYCf3dWaireO0PakLXMQLsc0IMAb8e3l-L1ZUKTFMhaW7CKnuKL7CCmtT-in4TjyLMLpzBP22e8W7qZNP1vz9IcY5knDR1xsip9sjzDsyqCfapNb8vW1A4jRhGhz7H61KfRrXrMMQbUVV7YauLjogKtPDqDPOYhEhAB5mARbYYzSmQsDsuEmE-XGhT41mKhblOQB35JuDB_1_Vrhfs6Dw"}], "types": ["park", "point_of_interest", "establishment"], "reference": "CmRSAAAAus0V3Ib_vpUdMPRxy7ZYkLepKC66_WtGUbH6gI2YLKUt-OP738-wJqIz9TI79rzgfrAkBAuKY8SVTzmggXCCOXIVFxUZgd_nIPlxTxt0A2mCPAt92r00p7E08oGb8BtsEhBIsQDdJbKys-5h_lVxz4uaGhROJZkgfDfA1MKxXMtluM7_fwfJ3g", "name": "Audubon Docent Guild", "rating": 5, "id": "7ddd5daf76cc4979e2ba6b062322d1c77d5d1c07", "job_title": "Acorn-International%2C-LLC-1", "place_id": "ChIJI9XyNFHbQIYRtwHb8EtTpeU", "address": "440 Wilchester Blvd, Houston, TX 77079, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.44932349999999, 29.7803218], "type": "Point"}, "properties": {"photos": [], "types": ["point_of_interest", "establishment"], "reference": "CmRSAAAAE5xAoQvCOzaWAlmHm7Rg_gObAJyCF_6jEy3Wl1fS9xxwPNffESAJqIdsRtRLH6UmhfF84nWQdd9qiXRGVCSYdAwqo-c2DnDlmsFWm8nV6z3eeH_UJ-2wdRQTKp6W3sfkEhAV8Y6_nGTohdJe1P2gziq1GhSRia9KhP4bOHIiIbtqOq3Gs1RTcg", "name": "Coastal Conservation Association-Tx", "rating": 3, "id": "7258b034e119f31e82320bca6e72781ee9f79d75", "job_title": "Clearpoint", "place_id": "ChIJcekacM_GQIYRPzL13cgQrPk", "address": "6919 Portwest Dr #100, Houston, TX 77024, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.47039, 29.655454], "type": "Point"}, "properties": {"photos": [{"width": 5312, "height": 2988, "html_attributions": ["<a href=\"https://maps.google.com/maps/contrib/101184977609161362375/photos\">aug4</a>"], "photo_reference": "CoQBdwAAAK7-eIZ73Oet_GJAQL0bvbvbXndnIP5q9tF1m7HNeiSzlyyxKR_sD7InUs7BU7IU6NeQCGoEC4SGpV_g7quOsR-rYNrW6xJeeHKr9A4R5FQe5AISn1g7WG6hQIY7za9ReiXgMBxRII3jWQY90YFK-9RxavJQ0N1t0LEuHMZRYXgAEhCne8tIK8FG6nzdJuIPTGUtGhR9q9uKDfwnrlJi2ewzJ1KkVxRb1Q"}], "types": ["park", "point_of_interest", "establishment"], "reference": "CmRRAAAAgUXpdlG9GMp1f5ySnCzZHXqHjWXnSSYKAQpqd3dhIqJkruSAvGsbFkcArH23xGo0nSv2lgcIdwPUufMAo0qAFlHBzaOJ7CVBNoZOz2RCDCbIluyoLX3jUXLcAYLJj8kdEhCOIAIjKrlwMbHCFMZaGFjSGhSkyeDjc_SewQEOMScOQyyZdBTdEA", "name": "Willow Waterhole Greenspace", "rating": 4.3, "id": "0127506e8071350c2d48f0ca56e939045297a0f4", "job_title": "Clearpoint", "place_id": "ChIJR6_2zTzqQIYRsA7wExgfDWs", "address": "S Willow Dr, Houston, TX 77035, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.4003322, 29.7388505], "type": "Point"}, "properties": {"photos": [{"width": 1136, "height": 640, "html_attributions": ["<a href=\"https://maps.google.com/maps/contrib/117056878997299689379/photos\">Marisol Brown</a>"], "photo_reference": "CoQBdwAAAEer7Pb7xIS-QpJo7fM-vilZfgJ1Gd5H4jNt9QGEfJUw80d3Ihx-hPsBXZng72EBlM-LwANWkEM1g5kkmNsyNuDtspt8Gp6f02jVrZpXN33z30HcXHE7VFkIeNbLkjcj_xFaUOXnymQWVXCAJIKgZXgXyzWz3AffqZ2_2DTy3YHrEhBxWxXYA5UVCS-uakR8wl72GhQSYp6kMJ1fIyd53BqFKxpj7pAPxw"}], "types": ["point_of_interest", "establishment"], "reference": "CmRRAAAAwtJwZ9X3qBNz2Ckldeqd6yFQbfF7HSASgQ2PbU3-9Ezo1Dg6knRcfwmrGWAbxjifBlst_18HNgx2mryU1Bdfd6CoNN0Xu2YUFeycbReYJTE9HH78MA5uK_S_iZF1zfc6EhAXE3jW6igsN33yHk5f8vLHGhRP36K1mcr3cHIyeApVk3QKxtbW4g", "name": "Masters Fine Art Conservation", "rating": 5, "id": "a462c2eef4e22ea319485ae7b84f3d20756cbdd1", "job_title": "Clearpoint", "place_id": "ChIJp8u2bZvAQIYRbosnWz6cVmY", "address": "1612 W Alabama St, Houston, TX 77006, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.3876169, 29.794149], "type": "Point"}, "properties": {"photos": [], "types": ["art_gallery", "point_of_interest", "establishment"], "reference": "CmRRAAAAT7eaIarJxRVMnmuPW43o3SWIx0AwODa9rkqr3gsqWI1GRs2sNBw5rRDlOzafr1NjND05f7TkAnl13IcuCLoYs8TpEmuTpVlYr0RpWOWC0NzD3we_Q3akRrVQZ2KjG4xHEhCrxRsvSYbXJDUUq0w7yxiFGhRdbmq1NGo-ZNDYE_xeyT3snT1l4A", "name": "Whitten & Proctor Fine Art Conservation", "rating": "NA", "id": "883a8c5ef35ab28e1630235ad65a6b16506a67fa", "job_title": "Clearpoint", "place_id": "ChIJ8YuXE6K4QIYRn1SF1hazFEw", "address": "1236 Studewood St, Houston, TX 77008, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.3858767, 29.7300997], "type": "Point"}, "properties": {"photos": [], "types": ["point_of_interest", "establishment"], "reference": "CmRSAAAAMlo5eqGo4lnB0WIR99ypKO4KVy4MOMoNtAJnD1zOgtoUhYAyD1HmJlz5l_i8J5HFlP8-zhBfa52p6oKz5duLhYVVpo-BEWOmdn9RKCQXC2B1R-FVvxl4BaRbXFiAZKwAEhCGCEV0_K4_ThcwdZEHVB_uGhQ4qtes-lj9l7KGHJltb9tT1vs6XA", "name": "St Mark Fine Arts Conservation", "rating": 5, "id": "ea2d4bac6d74716b33f456dff3aae0cc0b43cca3", "job_title": "Clearpoint", "place_id": "ChIJKbDEoXm_QIYRcRFBlp0dE8A", "address": "4901 Main St, Houston, TX 77002, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.483218, 29.7482286], "type": "Point"}, "properties": {"photos": [], "types": ["point_of_interest", "establishment"], "reference": "CmRRAAAATeYvXNfleaMzBUuvVNYqt3Sv8CTR6yqtvTf1KDTA_Fe1nc9mJs6fLCDCarRiMKKomTGdji_nBdKP8YYlB_nULS9eot3djjC3HHO1iKMseFRZw64dTSVbO_iNHhP8nFCGEhBj3F3_SkSvurWTGEyWCajpGhR3MZD6VwgaCPddbTHooSQOHWfMPQ", "name": "The Nature Conservancy", "rating": "NA", "id": "90af6fb9fb926dde9f7103577cebc4150bbb1dec", "job_title": "Clearpoint", "place_id": "ChIJq-m4EX3AQIYRJkn4Lhccp2E", "address": "1800 Augusta Dr #240, Houston, TX 77057, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.42318089999999, 29.7345943], "type": "Point"}, "properties": {"photos": [{"width": 750, "height": 437, "html_attributions": ["<a href=\"https://maps.google.com/maps/contrib/106788706324997826205/photos\">Erika</a>"], "photo_reference": "CoQBdwAAAGNs0JU6ME8qC2u6MCtBDx_U98RKd_QMX1Nw1wHFQRjdMmWdXZtWYc7l5HXoO4fZ27ZYrwu_5gpIa_fJBWz8X2UrVH9BddQ_pEOOcYpDOpDTZQEne904dATxvB8gJ1UXnrIl9GBRU1I49rL36cuLGue4BzvMXMeHrr9PhFzjxQ3mEhAxfGj-6tSV_fvDPxvIChvvGhR2aPQw2qtFC1bFTVektaJSHRzP-A"}], "types": ["point_of_interest", "establishment"], "reference": "CmRRAAAA4icQT3vLOd8eTK-fs24PP8fwoulc_EqcmxaaTl--Fbvv6cuMCkoSX1rrKynVbWHxDQDHfNz_kkTHARFsrGuv5ieYg2PkGbgx3XTyvvTfQelgdKvAtAUYmbDYr1IqOlRNEhAg93ywCzworAMcejwpijj_GhSUtbmJBGHBUQsVRkEeUN6wIbxXmw", "name": "Student Conservation Association", "rating": "NA", "id": "1c5ea7722fc0d99e9f7dfca55f5d9078224d51d3", "job_title": "Clearpoint", "place_id": "ChIJQcqBXfDAQIYRErawO-goGj4", "address": "2990 Richmond Ave Suite #400, Houston, TX 77098, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-96.038102, 30.055621], "type": "Point"}, "properties": {"photos": [{"width": 984, "height": 985, "html_attributions": ["<a href=\"https://maps.google.com/maps/contrib/110279808588468038448/photos\">Peckerwood Garden Conservation Foundation</a>"], "photo_reference": "CoQBdwAAAPVjcsAin2XupuBzC5Is5_TWv2WQgPA1EkVk6O2XFgZXOzpcjiejvrR-6YwtErTa7eDrogL_N_23EX747LytyreHxxTGrmbiEskjmjf4ztpd6-Y_viWwdgxy5A0y3oDcGQnSzJdaNwz5OniBMpkX9aYjoGzFtRWpntKSTNEm84sgEhCLpeE9nft8DXD3vahsBjAzGhRWBK6imYftPpPM6WMLYwBeFPA2sA"}], "types": ["park", "point_of_interest", "establishment"], "reference": "CmRRAAAARCVIWt-mr3JXs6prA2JIGuGCAUJAYuTHdRiiQsc6EPRUmnqrGq0I579samWXYLHk0ejxKoxCIohBZsjBydy_aY9OaViIkl4YU1nw7H3eLA0OW9sn5_IQKGZoisDv7Mz0EhAyXyS-ruq1i6PicK5iTyGJGhRMNCSVL3LW27dNEMNEbOp9QpiDFw", "name": "Peckerwood Garden Conservation Foundation", "rating": "NA", "id": "e618a4c618cd67ce4f5fdc165f640220ab3b53b2", "job_title": "Clearpoint", "place_id": "ChIJmUR7pvHKRoYRIIl0o73bPGE", "address": "20559 Fm 359 Rd, Pine Island, TX 77445, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.64386449999999, 29.7515036], "type": "Point"}, "properties": {"photos": [], "types": ["point_of_interest", "establishment"], "reference": "CmRRAAAARc5U8dlSzQrMpW5v9M3dTFJGGKU22b8wVMCD-3XLHsw7hm5ktpYnFIF7qV0lSoOCF3D9fE5qz-cgXnN0EMo_SJdnEAN2IdbAMaSYcFKD_EXZI8Vragmr_dD_Sw4o-sCHEhDrXEEIHnNMdcTUJPXG28_9GhQVp0AZkFTp28NEhZE_81R5yvvC4A", "name": "H2O Conservation Technology", "rating": "NA", "id": "30c07988ef8dfc62dac712b9d587daa4a36f2539", "job_title": "Clearpoint", "place_id": "ChIJIWZRKeHKQIYRXxta3wOMGGc", "address": "1725 Hwy 6, Houston, TX 77077, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.5705632, 29.7714443], "type": "Point"}, "properties": {"photos": [{"width": 3024, "height": 4032, "html_attributions": ["<a href=\"https://maps.google.com/maps/contrib/108143329814504597326/photos\">State from Jake farm</a>"], "photo_reference": "CoQBdwAAACWTYJ3PdjeOYNzbN4I4B73ApLNcbY4rWnqXlJgXC4o4TjNVeoNq4ApEhPbT22I8b-nJku91kI5KOQCYkyzkludaCpHNFBkE-7rt7W_rjX-er6pcQuvHPy-NQHHzskJXEVu4DLARVv1Qx56MtixS3ufFSnKYsUSSe1l6o1w0wA7EEhDUlDhHn01FXWhZ-ISD89vRGhQVSMFk7VsPU-nlMQ7P2BIwGOJQFw"}], "types": ["park", "point_of_interest", "establishment"], "reference": "CmRSAAAAzNVQlTRUmCI-ewf2ZffJQN_L32G6tc2bFt8Y3uiyXMiv-6GQaznHJHzxbniN5-gZUYmFkbsOZT2lbFf0moYLzop5vhIWdNuLuW3LSa9Na397HZe6yYj9PRj7kIsm9C2zEhClkot3-1QjFlpKH-tWUVB-GhT5JRZOQpdPZyFCgJSWlLWDqNmcAg", "name": "Houston Audubon Society", "rating": 5, "id": "050a5458d86bdd1cee7b09678bd6256d0a20a73e", "job_title": "Clearpoint", "place_id": "ChIJlQOxwVDbQIYR2uX_TZl0TYc", "address": "440 Wilchester Blvd, Houston, TX 77079, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.56820189999999, 29.770778], "type": "Point"}, "properties": {"photos": [{"width": 1800, "height": 1200, "html_attributions": ["<a href=\"https://maps.google.com/maps/contrib/108765250995932379967/photos\">Audubon Docent Guild</a>"], "photo_reference": "CoQBdwAAAGUTDDW6GUlMUqBvJWEuBoJL-yyc7gVnfpbRuW91kR636-K0s85-JKG_L4-Tk3AnaLtEefMy7F9rDbp0RP3GlMKqh1Xk4rvUwsp6-iTH7Kn3uYjmsIgClIuYs1DIotYsH70thRshvUG3kOzlrqCNG1B_YHIdGIpw0STusoqwGPKMEhAuQ6XamKie3LCewGIGpv3WGhRaHTMF5dy-86e55B6MSmcMHeQtqA"}], "types": ["park", "point_of_interest", "establishment"], "reference": "CmRSAAAA4b4sm1Jr85AsFTPJEaBNYhNYxl0AmTxkMkYnXKJatesBZZEk49-jshZj4cmUg0ieL-Uuo5E7gsLEjK00l02Djvk2ciJcZsDCbV1oXd6QrQV9FwEhb-VQiG-kLJFVvvToEhAEoDWQwrikbOnwteSYCYboGhQwB07zDbuRvP9RxMFVvDrdhk90FQ", "name": "Audubon Docent Guild", "rating": 5, "id": "7ddd5daf76cc4979e2ba6b062322d1c77d5d1c07", "job_title": "Clearpoint", "place_id": "ChIJI9XyNFHbQIYRtwHb8EtTpeU", "address": "440 Wilchester Blvd, Houston, TX 77079, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.44932349999999, 29.7803218], "type": "Point"}, "properties": {"photos": [], "types": ["point_of_interest", "establishment"], "reference": "CmRSAAAAeqYUd4BrHRgR0oMBAg8NgkK6YWpH3tfmoryUejcNTQI5aAJe7sSgHxVSiRbopMVqE7bhfC0ickOCwSzDGx9aQrbV6X6z6o8lWMEEUvMeFqVU38oyNTQGkOvsUWYOf30yEhAs_clsfS53tcyBMQqEObsWGhRXgxbmyueF-Y_0sRnhgT88xuuvnQ", "name": "Coastal Conservation Association-Tx", "rating": 3, "id": "7258b034e119f31e82320bca6e72781ee9f79d75", "job_title": "Paul-Davis-Emergency-Services-of-West-Houston", "place_id": "ChIJcekacM_GQIYRPzL13cgQrPk", "address": "6919 Portwest Dr #100, Houston, TX 77024, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.47039, 29.655454], "type": "Point"}, "properties": {"photos": [{"width": 5312, "height": 2988, "html_attributions": ["<a href=\"https://maps.google.com/maps/contrib/101184977609161362375/photos\">aug4</a>"], "photo_reference": "CoQBdwAAANLM_u2dh1d_1zB4PY74spuevbjBURxDQcAUL8Ojz_BaKol8tJRWVjP5I9uB-5Nz__NqGpFLJrVD-wzCMplGBNFE0QcUCyEQhcmhq6ggLKMx3kDJiZooRfb2vKHwmJz-uB878rXSUN1-qvCJpyAOaG57XcjkziZn1ns08wEAgESvEhAIeh5hCdWQDrCDOTxpKGPeGhRtvgts1p-qsNvmWKCXq_MA_hkvGw"}], "types": ["park", "point_of_interest", "establishment"], "reference": "CmRRAAAAFeVKibHLNt45FY-toeYWrzHNTJztX0HVqFAXiIy3Y6Xscqx_WX7T1ED5xtc-64A-EMvj8H1-g9FVRVXsqHdcQEmcJEymqosvstCSNGxkw8aU5L_HJc60Xc_XQRJJonEgEhAti1Yj4llLh30vjf9JmYS8GhTcS4Qd0z6Dt4TwsVTtm_LmxsBpaw", "name": "Willow Waterhole Greenspace", "rating": 4.3, "id": "0127506e8071350c2d48f0ca56e939045297a0f4", "job_title": "Paul-Davis-Emergency-Services-of-West-Houston", "place_id": "ChIJR6_2zTzqQIYRsA7wExgfDWs", "address": "S Willow Dr, Houston, TX 77035, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.4003322, 29.7388505], "type": "Point"}, "properties": {"photos": [{"width": 1136, "height": 640, "html_attributions": ["<a href=\"https://maps.google.com/maps/contrib/117056878997299689379/photos\">Marisol Brown</a>"], "photo_reference": "CoQBdwAAAOgyg9kxJP1T1B2ew4Osn9uaksO2Dr-g_DeDWfVoWO1XuacROfDvB6tFAUdIUBZ-LfY2U1ux4cFOnOW1MNJx9sPTIuUpytMpgBFb1InWSY8LLItljXt-Nl5ajXqm5DCp8jtBBQTsElt0_rHyeKts4WW-rPSPSG-qBEsWeQEQHkSsEhAeRzpr0XFB5eFWgp_poqSkGhRQVnEzaKHC2vPrgeWYakWoxdyicw"}], "types": ["point_of_interest", "establishment"], "reference": "CmRRAAAALJUTASANkrn4F6wUjHZTsOfPEv2flvs-25AXga5WURlGAdJhnCeWSCKweIFvuqV0R4yGxwctjXKUCSXZgYq9r56jwOEyTtmrYilEbZtdIW94BvHyV1ft29TKBtvmuqsPEhDzlTKckrLjn_9mkHbIY1l-GhQhX9Xsm-wURWAoptshXL6QnB0snQ", "name": "Masters Fine Art Conservation", "rating": 5, "id": "a462c2eef4e22ea319485ae7b84f3d20756cbdd1", "job_title": "Paul-Davis-Emergency-Services-of-West-Houston", "place_id": "ChIJp8u2bZvAQIYRbosnWz6cVmY", "address": "1612 W Alabama St, Houston, TX 77006, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.3876169, 29.794149], "type": "Point"}, "properties": {"photos": [], "types": ["art_gallery", "point_of_interest", "establishment"], "reference": "CmRRAAAACJ7aGMVW72-VMNt4BPLJTbIIgViuUM1X-7zgmt1CTlu0dQawrUdaCdIFAe4GuX19BUkcYg8w_7CMP0oI5SvokX5nCwedWwlSxoP6brxTmMxCBBB72jrsIwNeLVjibbS2EhA408t8Xy110_f-7KddRcXkGhQA4arc6VV2KAbEGYYWQ3AbdJ6QUA", "name": "Whitten & Proctor Fine Art Conservation", "rating": "NA", "id": "883a8c5ef35ab28e1630235ad65a6b16506a67fa", "job_title": "Paul-Davis-Emergency-Services-of-West-Houston", "place_id": "ChIJ8YuXE6K4QIYRn1SF1hazFEw", "address": "1236 Studewood St, Houston, TX 77008, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.3858767, 29.7300997], "type": "Point"}, "properties": {"photos": [], "types": ["point_of_interest", "establishment"], "reference": "CmRSAAAAbYSGPVH0zYFpE9Lt2_w4UZjIaIixSSB2ATRWibsqICEbSS5H3awO7bXFaV81yOaDcze-mMU2VtRnR7VrJkbGML6OvH3F8r3H9Drbq8USTeh3ALu7IfPA0un5lmUnlFeFEhDR79LAqI807tE7uJB-u9_jGhShQZPPljdGnXyeYrmIpXzr5bUn9w", "name": "St Mark Fine Arts Conservation", "rating": 5, "id": "ea2d4bac6d74716b33f456dff3aae0cc0b43cca3", "job_title": "Paul-Davis-Emergency-Services-of-West-Houston", "place_id": "ChIJKbDEoXm_QIYRcRFBlp0dE8A", "address": "4901 Main St, Houston, TX 77002, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.483218, 29.7482286], "type": "Point"}, "properties": {"photos": [], "types": ["point_of_interest", "establishment"], "reference": "CmRRAAAATkKxVj1TewtVp-L0zwdRkn3nc6Xakc0EPqcjwl1KPa3Zhaeh2K7qMF0ocgCzh9JJgtkUdcim9EHXNLEnV8t4dflO89BFK3Igtp0laIbD_pDLel1RvnEIAqkychuQxds8EhAWPDotwEkP8RYauAJJSi_cGhRDKIeOJKTojLgthB5tEkhg46XNTA", "name": "The Nature Conservancy", "rating": "NA", "id": "90af6fb9fb926dde9f7103577cebc4150bbb1dec", "job_title": "Paul-Davis-Emergency-Services-of-West-Houston", "place_id": "ChIJq-m4EX3AQIYRJkn4Lhccp2E", "address": "1800 Augusta Dr #240, Houston, TX 77057, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.42318089999999, 29.7345943], "type": "Point"}, "properties": {"photos": [{"width": 750, "height": 437, "html_attributions": ["<a href=\"https://maps.google.com/maps/contrib/106788706324997826205/photos\">Erika</a>"], "photo_reference": "CoQBdwAAADDA93Ra7HmGNhBkPeAbAdgVgpTOUbA3vMMzYqVjHzahC5e9S1aBdCXo8f3NdAehppVphZdcl1UD1tEo-AMsrQgTToNyhg4idIPdJXilyW6lWLnYZ6mmyYZyoz69GMIJu7_EW1CegPts4NRt09lzj8d8XOqqtz-K718dEF7Vm-jhEhC4nbBji4GecaejGzMXwFsMGhR7J20i8gjqoBPgfA9Vu1aaUH3VLw"}], "types": ["point_of_interest", "establishment"], "reference": "CmRRAAAAwnbPww_fpV8tqRwgRHGTtiUW-BsSbCufCzme6L4afmWPCJy4hlthhkcoGM0r6pD43wM3wbrH-r1FAI6tHP5Gq5S0N8uPdc3iCPwTl0YceKOgzT8QRdNuri02ZJ6FMRKzEhDJ-PKjpSyubTekCaypvvvXGhQ-KJP1vY4bku-3I29zoL3NV2T2NQ", "name": "Student Conservation Association", "rating": "NA", "id": "1c5ea7722fc0d99e9f7dfca55f5d9078224d51d3", "job_title": "Paul-Davis-Emergency-Services-of-West-Houston", "place_id": "ChIJQcqBXfDAQIYRErawO-goGj4", "address": "2990 Richmond Ave Suite #400, Houston, TX 77098, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-96.038102, 30.055621], "type": "Point"}, "properties": {"photos": [{"width": 984, "height": 985, "html_attributions": ["<a href=\"https://maps.google.com/maps/contrib/110279808588468038448/photos\">Peckerwood Garden Conservation Foundation</a>"], "photo_reference": "CoQBdwAAAHlPeulfnTudmR4KyNqsCMHmHA1WZhd56HACCMb20ZZb7cT7BHL-mYuckYtcQoWkXNx3bb6ZDJtcUwhL32alNPP9AgAH1WaRj4iOcvNkDQnMob5HKkXmbRpsQa7dGywUJNZKBU27MXVCTOMJO6oUULjmIf68qnBrFG955kwKeRC_EhAdKLqrgY8ZT-ZOr0d8KXFEGhQNu19DuFLZquhOujl7FCAhu5hpMw"}], "types": ["park", "point_of_interest", "establishment"], "reference": "CmRRAAAAks8uqYMJJPN_r5PL5BM9sDX9PXt5sTFZCPp8hpFdxMLQHDnnabda4WhTPK7mF6SdHbSs14ix4WJ1VYHc8Jb9I_w2Kk-UivT43DFJgjqAZLH52bT-1lDGa163Zh_wnFucEhDfFinHLgs7kOX5DsdX4LmeGhQhjzKklVjoDiEBT1Ka7kmGyfeR3Q", "name": "Peckerwood Garden Conservation Foundation", "rating": "NA", "id": "e618a4c618cd67ce4f5fdc165f640220ab3b53b2", "job_title": "Paul-Davis-Emergency-Services-of-West-Houston", "place_id": "ChIJmUR7pvHKRoYRIIl0o73bPGE", "address": "20559 Fm 359 Rd, Pine Island, TX 77445, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.64386449999999, 29.7515036], "type": "Point"}, "properties": {"photos": [], "types": ["point_of_interest", "establishment"], "reference": "CmRRAAAACMunxcT1HNtCdWeB2Ob_fuPb-FEESK8v8Dif7kJGaJVEoyo6D1ZZFUlhTWsskGROiGtO54QUaADExAivIp_J4lhCMBnZQRRBI6SGNdyyLv3w-0o2zSU2iu5G_vmJjvvbEhAmD19UZUx392zahQbbaUrpGhRNuIxLT3IgChvi6G_bJpK6Q9hJ3A", "name": "H2O Conservation Technology", "rating": "NA", "id": "30c07988ef8dfc62dac712b9d587daa4a36f2539", "job_title": "Paul-Davis-Emergency-Services-of-West-Houston", "place_id": "ChIJIWZRKeHKQIYRXxta3wOMGGc", "address": "1725 Hwy 6, Houston, TX 77077, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.5705632, 29.7714443], "type": "Point"}, "properties": {"photos": [{"width": 3024, "height": 4032, "html_attributions": ["<a href=\"https://maps.google.com/maps/contrib/108143329814504597326/photos\">State from Jake farm</a>"], "photo_reference": "CoQBdwAAAGvu1xZ_rjqwSY9QUiNb0khJjwJOYQD4u92cCHD6olkFx5whECoDmoCFDnvw_FRBmgPSDhp2OTafopAhVGsBJeQaFBjBlS2gW2rXXJfa4PH6xDcE6LpOp85vmSLRt3MjxavHCnaPKIiPENErL3GT5u5ZTSra6RHcuQanLp71jazbEhBv3f0GYknCkAlRGmP49WGDGhRCW4_MaB_hdt7vL7t_QiLdVMIJdQ"}], "types": ["park", "point_of_interest", "establishment"], "reference": "CmRSAAAAos8AGWgTw-jmX7RgX1M0MesCTyqRR9kwLY-amj2d1te_34xf8SoNDK1fWcrOOlU78BM69mWiKTA1cOrXrnhEzEyp5iJrSUUgK59knsGEPqPjbLn-6CIFn3HK0PLeCpTsEhCIr46a4UKPQB3uWvd3mMcIGhRQLhLJoxQZcmWaJI9noxqFSuYWmA", "name": "Houston Audubon Society", "rating": 5, "id": "050a5458d86bdd1cee7b09678bd6256d0a20a73e", "job_title": "Paul-Davis-Emergency-Services-of-West-Houston", "place_id": "ChIJlQOxwVDbQIYR2uX_TZl0TYc", "address": "440 Wilchester Blvd, Houston, TX 77079, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.56820189999999, 29.770778], "type": "Point"}, "properties": {"photos": [{"width": 1800, "height": 1200, "html_attributions": ["<a href=\"https://maps.google.com/maps/contrib/108765250995932379967/photos\">Audubon Docent Guild</a>"], "photo_reference": "CoQBdwAAAHLYwN0J-8NI0f9GHVZZExFaODjkgic2wmpl0qAslHNtEkjOZubQVw_vAFvLuTdGJhzmViYCClPy4PS4eoszmwOUrcdRcXFJGhAUx0kbWWN8po48F-YnyIrRF7UexQ5BVDFRLJLmKzAjFBPd2L-gbpAd89rYxEnYgPsUb-jA1f-WEhDFnsqbNK-wL48blshohcf3GhQPMXfywtadFYtui8rslaZ7Q14dMg"}], "types": ["park", "point_of_interest", "establishment"], "reference": "CmRSAAAAGxj9dqxqzEJLAzUA-wnfGaNL1X9Qwbi3KEB0PDAcWZsiny78Qy5uVREn5mIAtNHIQ-_RkNp8dgCRnv0UX4W7Y6Iw4Or4CDbUmScg5LVbIlGd9dFu6HrCl-hjFYf3M8fgEhDak3-S5QYkIMRT-gTAyNAMGhShSgIgPCz5c_IoZ9RZ2vDwIzGl9g", "name": "Audubon Docent Guild", "rating": 5, "id": "7ddd5daf76cc4979e2ba6b062322d1c77d5d1c07", "job_title": "Paul-Davis-Emergency-Services-of-West-Houston", "place_id": "ChIJI9XyNFHbQIYRtwHb8EtTpeU", "address": "440 Wilchester Blvd, Houston, TX 77079, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.44932349999999, 29.7803218], "type": "Point"}, "properties": {"photos": [], "types": ["point_of_interest", "establishment"], "reference": "CmRSAAAAdQwJf96KmdAQQI9oQsIfnLf-JXUme3T63uGPPm2_VB8J42fc0R1seZAe1nhttqFzT4ACwnmxqaktSy-EWc9n-YdHUquEOEvgBgCIg0TepHj_hHvP0EvXyYye0jb0ezvHEhCGnQ6neN30a-znG-GXHqmuGhSl4CqS_mNZSID8ZVr-IxavtpaQ_A", "name": "Coastal Conservation Association-Tx", "rating": 3, "id": "7258b034e119f31e82320bca6e72781ee9f79d75", "job_title": "Hhs", "place_id": "ChIJcekacM_GQIYRPzL13cgQrPk", "address": "6919 Portwest Dr #100, Houston, TX 77024, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.47039, 29.655454], "type": "Point"}, "properties": {"photos": [{"width": 5312, "height": 2988, "html_attributions": ["<a href=\"https://maps.google.com/maps/contrib/101184977609161362375/photos\">aug4</a>"], "photo_reference": "CoQBdwAAAIvo2L0jt1S6vsjt6GyaEvNj8TfsD_tZ__JBrpNcaJGwkp2VRZZPdPtWP-8ht41d0vHAbf0mB9rj0nojg5FsSxu2DLPFLMiqGez9r0twZSQ6bXmHEprFZTY5ITMlh8GvoWc4OQ49cy6ol0iIT0EVVQ5ICtQ6Kik-B0bskqTFRkrWEhDroGfQO4jM_630RJdliMG1GhQLuuQSKFt3gfz8eiunb8OqkEj7LQ"}], "types": ["park", "point_of_interest", "establishment"], "reference": "CmRRAAAAiFJhvmLq3wa84IgLC0xoN-F-c7wKxXE7KXqwO3Drl6ifjS5PInP9VIBfS64L5_SduVnfL3EurOzr4eHeLTZbpO0Z9X8B27AG9GOZkMd8MzYjAqqEE3hUaw7j5OZZ_CqLEhCfGaWCrT8TKN4DDcsj-kEOGhQ2V5QvJl6ObSvjiQNlVVsK_su0xQ", "name": "Willow Waterhole Greenspace", "rating": 4.3, "id": "0127506e8071350c2d48f0ca56e939045297a0f4", "job_title": "Hhs", "place_id": "ChIJR6_2zTzqQIYRsA7wExgfDWs", "address": "S Willow Dr, Houston, TX 77035, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.4003322, 29.7388505], "type": "Point"}, "properties": {"photos": [{"width": 1136, "height": 640, "html_attributions": ["<a href=\"https://maps.google.com/maps/contrib/117056878997299689379/photos\">Marisol Brown</a>"], "photo_reference": "CoQBdwAAAMnp7Mb86gvAlPMzHQhuEdbh_g0-BdjYd94vBmwjCLaMnKd9lYognHaEh4cIy9JjXATiWM_ld6rLuhkHorcLAB9-3jG6NgPLIyao5JrqGkoEMDFB6FqBS15iRu3f-4gHaoYFTDlfalDKcSs1jQQJhe2upNmDpkHutyvYaYqceHdpEhDbX6VkCSIoZ4JReYokgrJNGhRbmkfC5T3AXqQHzP3vouGgl70LBw"}], "types": ["point_of_interest", "establishment"], "reference": "CmRRAAAA_fMLSVWYzkVxWGDj1lx3x99fdY2QuMWiEkUVHzv06Wq9JpYTqGEtCwkskLIcgB6-80iLK64RDDn27WMtLBSn-3AzHSY6Kpc52A2C9iLAwfJzzPzVTfDvsQJ0hyLGqBA5EhChqCFmkcN4Meg3hcEq07bWGhRA3JmyZQW-a0u3qCTGHXceoATt0Q", "name": "Masters Fine Art Conservation", "rating": 5, "id": "a462c2eef4e22ea319485ae7b84f3d20756cbdd1", "job_title": "Hhs", "place_id": "ChIJp8u2bZvAQIYRbosnWz6cVmY", "address": "1612 W Alabama St, Houston, TX 77006, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.3876169, 29.794149], "type": "Point"}, "properties": {"photos": [], "types": ["art_gallery", "point_of_interest", "establishment"], "reference": "CmRRAAAAz0Jw5jIqhm8mNJqpknWeF9DziO5zeeWQ5hE4kuDq9eyrT3LLWi-gOcWzCgo9gZkBY_atTNW3tmanUXrkOpPVi5nP6WEnCDAiAbejJ6Z-hjcXE9sPl2m5mAv2IMRNEq98EhD78g76TLpYVW2yKuUrPxthGhR9oLJ7UAsWNSJJ3MbUUBwuk5fk3w", "name": "Whitten & Proctor Fine Art Conservation", "rating": "NA", "id": "883a8c5ef35ab28e1630235ad65a6b16506a67fa", "job_title": "Hhs", "place_id": "ChIJ8YuXE6K4QIYRn1SF1hazFEw", "address": "1236 Studewood St, Houston, TX 77008, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.3858767, 29.7300997], "type": "Point"}, "properties": {"photos": [], "types": ["point_of_interest", "establishment"], "reference": "CmRSAAAA3F9taa4tPRGfxXMqTWjFpfrYFRgOwicbNAOAzygh8RAU_NkFBq6pGP69Nr1pptV7hCJpcsOeUIybJsHPL2Kpp7bUXGNeex4131DSmLVo895TY3H_Ns0ywDmXLmNjAxOMEhA6tuLY5DcLaRECKoprRe09GhTY8NOl9a6qSq_OV9lx1kr2Qi62KA", "name": "St Mark Fine Arts Conservation", "rating": 5, "id": "ea2d4bac6d74716b33f456dff3aae0cc0b43cca3", "job_title": "Hhs", "place_id": "ChIJKbDEoXm_QIYRcRFBlp0dE8A", "address": "4901 Main St, Houston, TX 77002, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.483218, 29.7482286], "type": "Point"}, "properties": {"photos": [], "types": ["point_of_interest", "establishment"], "reference": "CmRRAAAAM81vIIr6-F6MGZPhGW3FIzQmZ_ith0wMzJ4AQ6lH5zg8y6ERmBRxSzysD9Mc1eRpGK0qFOgiBdikMBLLxbC0rieveg1lfj8iMC2NABULVK1N0JUOurOcPbYxDaFs-2nwEhCeyY1P_qHULs1G2TXPwX1RGhQIbod789TuB5dwA6aepciYjRNQDQ", "name": "The Nature Conservancy", "rating": "NA", "id": "90af6fb9fb926dde9f7103577cebc4150bbb1dec", "job_title": "Hhs", "place_id": "ChIJq-m4EX3AQIYRJkn4Lhccp2E", "address": "1800 Augusta Dr #240, Houston, TX 77057, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.42318089999999, 29.7345943], "type": "Point"}, "properties": {"photos": [{"width": 750, "height": 437, "html_attributions": ["<a href=\"https://maps.google.com/maps/contrib/106788706324997826205/photos\">Erika</a>"], "photo_reference": "CoQBdwAAAP1k2ByL0EE7ydaEtjajxgDyqKJnNVl-vn-tEUdNfT6jKjApN8Wdft4ESODXG9HnQzHIzTE6-OZ_pwforIZYeBXOI6NF-bZVl6xKRht1GF6ONXbjfTFg260GRcuOSi0Ohg03otC6KIrC4136CUY2IKWoGnLTrNw66eP5TorUZLuDEhDOfcAKNVSvHBLx2I3L56YAGhQJ9B7M-2mYqt-Pa3kguMAc6NStcQ"}], "types": ["point_of_interest", "establishment"], "reference": "CmRRAAAAUk_42_scm9HAk52nj2CXkrnZ6H2RHV1aPTmbPgUyAVc5D5bvzCiIcxzERo6M0kArZn2u8omsaZtXeIOP75AkW53zRiGE7gVgtCn_ehOFXqyhb71j_uhK3_Sbvx-NShx7EhC8WsPeiSiHJTJ6cL8WYcd2GhS-yDlyvbpCVybvzGK6YnHnVAmhYQ", "name": "Student Conservation Association", "rating": "NA", "id": "1c5ea7722fc0d99e9f7dfca55f5d9078224d51d3", "job_title": "Hhs", "place_id": "ChIJQcqBXfDAQIYRErawO-goGj4", "address": "2990 Richmond Ave Suite #400, Houston, TX 77098, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-96.038102, 30.055621], "type": "Point"}, "properties": {"photos": [{"width": 984, "height": 985, "html_attributions": ["<a href=\"https://maps.google.com/maps/contrib/110279808588468038448/photos\">Peckerwood Garden Conservation Foundation</a>"], "photo_reference": "CoQBdwAAAIjn-Mv02-kD3UsvCVtdCGoobU0WIjykQK2z48kf20sd8B4XpFFwtIM9PBk3abQRMlcfAHBNKrGGa1RRoDEzKGSvz5ale4opFl-3MbkD0smvSA5OXOLVEUM69lT_hHz7ZXv3TX-pIOPOv0vGt4jxKNWvr-Fo_jpu_AAccm29AriTEhBHcfmaHr1YViIjZSuPSH-1GhRno_UtuPFPQCeen3LYPFOoKoDKjg"}], "types": ["park", "point_of_interest", "establishment"], "reference": "CmRRAAAAqNa0Plza_ia8kNFJftQa6sISAPYQSUhzpBYyFRl1BWr5uJtQEFbBc9GA_hdsWgHN-qwE3IzNckgGGQoHBGvSkQrNfseBXB8ZpkL-bPRSv623GhTxl29qM8GQkiu20H69EhAw7Fw1a5Z8M5I7kVGwdd3sGhQbInP1mGgV4dVuyC9xrW9zfqv2WA", "name": "Peckerwood Garden Conservation Foundation", "rating": "NA", "id": "e618a4c618cd67ce4f5fdc165f640220ab3b53b2", "job_title": "Hhs", "place_id": "ChIJmUR7pvHKRoYRIIl0o73bPGE", "address": "20559 Fm 359 Rd, Pine Island, TX 77445, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.64386449999999, 29.7515036], "type": "Point"}, "properties": {"photos": [], "types": ["point_of_interest", "establishment"], "reference": "CmRRAAAAMcWwY03wvJRuaFPtVTO9TM5t3Av3TknzI-3vs3RFpmzrdB8-SceZ_Dbc6WQreAwZxGYq-XwaZUq0bnFNjDbPOzq5ElRD0wKm_92TOWo5jpS63rP0YIz5RSz4ByIir17GEhBvJxKJdgwS_9G85VSjbgQ7GhTiBOGC1S_OjfFqOtmosPWAfFh9aA", "name": "H2O Conservation Technology", "rating": "NA", "id": "30c07988ef8dfc62dac712b9d587daa4a36f2539", "job_title": "Hhs", "place_id": "ChIJIWZRKeHKQIYRXxta3wOMGGc", "address": "1725 Hwy 6, Houston, TX 77077, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.5705632, 29.7714443], "type": "Point"}, "properties": {"photos": [{"width": 3024, "height": 4032, "html_attributions": ["<a href=\"https://maps.google.com/maps/contrib/108143329814504597326/photos\">State from Jake farm</a>"], "photo_reference": "CoQBdwAAADtpcc0j4KyhtUQ1_CKUn2sJufz8UJfp8jHWdfX0DCj8JsI7LiyppjnhC4lL1xUAm08dPaz5Har7qr1EztMDcBkYPMsNv2Bk2TBk35H9e2RBMQC8VUuPboWGe0hmOWV6qyJZ_sbwwLEmjHfvOmIPfxCxUiw9dVpOGUiGx3Iq6-ExEhD_pw6HDo8TwXYyRPWj0ldTGhQYGgdYzmp_RTqhPn5gChgq91lWPg"}], "types": ["park", "point_of_interest", "establishment"], "reference": "CmRSAAAAjYTH_x1nuEoXY3ZGQpHhIguRrLsQ6eSGf8sTLtYH1wHD6cEMAghduuxpuHJdvHOC_b3Im-Pof4rKowD8M1EYM9HUVlZ-iZx4tNVW0XPSLNX3HOzRKvrznJA6toUpF6z1EhBjpzblQSatlcL9g7xhiCJHGhQDi7C2_MMH1t6Rvbbx1nFhhqSoIA", "name": "Houston Audubon Society", "rating": 5, "id": "050a5458d86bdd1cee7b09678bd6256d0a20a73e", "job_title": "Hhs", "place_id": "ChIJlQOxwVDbQIYR2uX_TZl0TYc", "address": "440 Wilchester Blvd, Houston, TX 77079, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.56820189999999, 29.770778], "type": "Point"}, "properties": {"photos": [{"width": 1800, "height": 1200, "html_attributions": ["<a href=\"https://maps.google.com/maps/contrib/108765250995932379967/photos\">Audubon Docent Guild</a>"], "photo_reference": "CoQBdwAAADgrx0LEpX8X2HbTU_xnM9AhoFu4dl1uHRZESM0xCLyDRuZO70YsHV4tuNmn_clbmnUut97R5HpjwwxEUFnZTUqOObj1GujGIrtQqe6UxF_UWV14MEbu4tUOoODOX74JV6GPkwbdoo0z8z__yDp7mW16OgIMOjfhiQ-AKO1m0Jx3EhBJQBxrsc0YWT3WIKDQKVu_GhTcSqAKoOdeA7Q_WpZxK4HsElwESw"}], "types": ["park", "point_of_interest", "establishment"], "reference": "CmRSAAAARFhzzmnX3hfwZHCdwp_UVOswcokMxQO_luJm6Ybt8lvBzY9lptwV1Wn7xgawX5J4Eh8BsDRiMKI9K0DAzqftMlBtx-SE0ckjpx69TY6XPUgQ3fdYc-knl_7BBDS5w40LEhDXLaPDm00rDkiLJquTMJraGhQX37cvBz1eMmm1365UxsJWITDbGw", "name": "Audubon Docent Guild", "rating": 5, "id": "7ddd5daf76cc4979e2ba6b062322d1c77d5d1c07", "job_title": "Hhs", "place_id": "ChIJI9XyNFHbQIYRtwHb8EtTpeU", "address": "440 Wilchester Blvd, Houston, TX 77079, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.44932349999999, 29.7803218], "type": "Point"}, "properties": {"photos": [], "types": ["point_of_interest", "establishment"], "reference": "CmRSAAAAjVZ-HXbl-NhmPWIp19uhlsIfDHdGkHfoFkZJUj1p3eQjaa8rAO96abqJjyEGxdPN9dtba3Rj5Y2-AKocCHOT9OHN60Ztw2ucASzbQU0qZqg4zhIHGcgplCpCQwyMU0V4EhBgWb_q0KXledvAbv-W8g9zGhRHMH6Vfz2Fx0X-rRWm8HE8cA40ig", "name": "Coastal Conservation Association-Tx", "rating": 3, "id": "7258b034e119f31e82320bca6e72781ee9f79d75", "job_title": "Gullett-%26-Associates", "place_id": "ChIJcekacM_GQIYRPzL13cgQrPk", "address": "6919 Portwest Dr #100, Houston, TX 77024, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.47039, 29.655454], "type": "Point"}, "properties": {"photos": [{"width": 5312, "height": 2988, "html_attributions": ["<a href=\"https://maps.google.com/maps/contrib/101184977609161362375/photos\">aug4</a>"], "photo_reference": "CoQBdwAAAA1H6RcCaAw-dlo6aqMqQlSoyXZpVin8PxU6_Z5D54CdUF7bxGI3QtkW3uQQw5IU5_aVGeG3M3d1jrVXoe4lnkO1PO0d4EqGvLaeVmmrm8LUGFM9DphrwjalBxUhDIg4oHmkItwA_kGh8yq2uOHTKfIK2oO-94j_daKWXBqjSW6uEhAth3KtEmU2V73EnajvZ2NRGhQqtEz7t7xFy3pVIH7Lb9QvuY-Ssg"}], "types": ["park", "point_of_interest", "establishment"], "reference": "CmRRAAAAUwBxDBhWXPk_c6en2vSWFxzyxaqoX3wEKgPfAuei42vwfV0iXiTInX4VXEiFa05hE0HuKIrQ3cnQhYbFPBXsBPpXNceebtkxBmWZ7ngj1rcuhK7kGgzLhlUXcmZxlWSrEhBFKZeXzhmWbsXVmnhjazSkGhSEoHF28vZiOtEb9TKHL_05FAMGxg", "name": "Willow Waterhole Greenspace", "rating": 4.3, "id": "0127506e8071350c2d48f0ca56e939045297a0f4", "job_title": "Gullett-%26-Associates", "place_id": "ChIJR6_2zTzqQIYRsA7wExgfDWs", "address": "S Willow Dr, Houston, TX 77035, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.4003322, 29.7388505], "type": "Point"}, "properties": {"photos": [{"width": 1136, "height": 640, "html_attributions": ["<a href=\"https://maps.google.com/maps/contrib/117056878997299689379/photos\">Marisol Brown</a>"], "photo_reference": "CoQBdwAAAKgSjxMCawS3ascqKA9ITQLTDZWAjgeNZK9axRh99HRI_yMmKKD0S3GGhG7mZ9Gt827QkYc6nCIr-te-TD_gWj37leR4LmdZ7Ov8r_SrdYbpWjL2zbFot_u4YUB6LjhMZcqFwr70pLelBCDo0nyb8-VJNssJGqaXOwrwZlOdNS8nEhBY9XJTjpBnLAlwyhT7Nl-qGhT9uMpz-VXA9E3vJmdjqrQYhYxvGA"}], "types": ["point_of_interest", "establishment"], "reference": "CmRRAAAAHZuO1pUaRwi8u29YuSoN8n40SO2oGLGxEyEjCP3_fS-RJP5Qa1vDw4Ye0RaoeyMgY6SLw7YdTkbAGyNUMGv-xis1GuOjfqFENmPRuLGS9AUNkQ3Dnh16qqOPd1gB1u4GEhDX3iQj__9prD7oyIcTkHPkGhQeFBahy0-dN2SgeX1NRnQQ2npe3Q", "name": "Masters Fine Art Conservation", "rating": 5, "id": "a462c2eef4e22ea319485ae7b84f3d20756cbdd1", "job_title": "Gullett-%26-Associates", "place_id": "ChIJp8u2bZvAQIYRbosnWz6cVmY", "address": "1612 W Alabama St, Houston, TX 77006, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.3876169, 29.794149], "type": "Point"}, "properties": {"photos": [], "types": ["art_gallery", "point_of_interest", "establishment"], "reference": "CmRRAAAADwFpoAeRp3drawT2NLefIvb6zwCvqBnfn2Yw7QzdNlD-HH1h2QvzufDM7iM7uIEYQ7TmGeCf-5aCzesVdceznaJbDgC1dTpw-xAZuLNtBuba9TZmJrF-4fUU2dBDoDyFEhDC9E7Znrewl1S6Mao26lp7GhTuWQUz2ueQfAnjfG9xPfBaxI_yIA", "name": "Whitten & Proctor Fine Art Conservation", "rating": "NA", "id": "883a8c5ef35ab28e1630235ad65a6b16506a67fa", "job_title": "Gullett-%26-Associates", "place_id": "ChIJ8YuXE6K4QIYRn1SF1hazFEw", "address": "1236 Studewood St, Houston, TX 77008, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.3858767, 29.7300997], "type": "Point"}, "properties": {"photos": [], "types": ["point_of_interest", "establishment"], "reference": "CmRSAAAAouBxEQ0mRmxUY9bIfi_FgikMEtAYlwHWHtq_qQKyMIwxIFctKkX4OUEyucBD_PKWPAENIpuMvPFshQDuX0K_HIrl5-IHAxOrCLBRCsK5RrEfgOPjvkvq7ZY_OyfnZ0zaEhAeRxof1C4iD6iWAdlBDWOaGhTCwWObALYiLQa34mvJOfOhwB5GMg", "name": "St Mark Fine Arts Conservation", "rating": 5, "id": "ea2d4bac6d74716b33f456dff3aae0cc0b43cca3", "job_title": "Gullett-%26-Associates", "place_id": "ChIJKbDEoXm_QIYRcRFBlp0dE8A", "address": "4901 Main St, Houston, TX 77002, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.483218, 29.7482286], "type": "Point"}, "properties": {"photos": [], "types": ["point_of_interest", "establishment"], "reference": "CmRRAAAASOGYixsQCdRHOdycnSMpuvsQe9arImXSPNlHjTKR5o7RbFXBEM6EiAYxPrLxatlT5shFnGw2cihmoN_HB-b-bLUV-4csaCYxjkezLnlcmS2cApzHQJ4XtgIuSwQJJUgWEhDVZ_IRyY2HtJ5Gh55mBj66GhQVcA2M--G_kpmbbMKhRwQKsHzbfw", "name": "The Nature Conservancy", "rating": "NA", "id": "90af6fb9fb926dde9f7103577cebc4150bbb1dec", "job_title": "Gullett-%26-Associates", "place_id": "ChIJq-m4EX3AQIYRJkn4Lhccp2E", "address": "1800 Augusta Dr #240, Houston, TX 77057, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.42318089999999, 29.7345943], "type": "Point"}, "properties": {"photos": [{"width": 750, "height": 437, "html_attributions": ["<a href=\"https://maps.google.com/maps/contrib/106788706324997826205/photos\">Erika</a>"], "photo_reference": "CoQBdwAAAJo0Eufpd7H1ardEhjC-nBS6hm5JLH6iIGLmkh7TXe3sck331F0RGagoyJa6qKiLVSRVA1zSLDNf2GfjNdcyqIq3CS5gCcZ9iMVktlk72UMh9zrvF2lLn2ivbb4dr65Qiyds-1MKZlV7j19tNE5psxeDVHNAfddVr6nu-fBgJdnQEhDCuD8qNWLz0zajkBjKoSHRGhQAfrjC8zt-wrz8PgLwYcJUILtrFA"}], "types": ["point_of_interest", "establishment"], "reference": "CmRRAAAAyQY6JZGmVlRxAHCmXSME9x6DYmJoYzv3PsxiCcOBNcNsNkUppGgYT34DlVTAsrsdMCk-hiBN7nsz8_01dlPRe5Nen6uFU9sMYOCheJxJH2eLfi_vfDvohyTUtO1kip1uEhBg03519O6SwvfHLLXi34L9GhT98yLzjtXeP5TY1Hnj2l66INUc6w", "name": "Student Conservation Association", "rating": "NA", "id": "1c5ea7722fc0d99e9f7dfca55f5d9078224d51d3", "job_title": "Gullett-%26-Associates", "place_id": "ChIJQcqBXfDAQIYRErawO-goGj4", "address": "2990 Richmond Ave Suite #400, Houston, TX 77098, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-96.038102, 30.055621], "type": "Point"}, "properties": {"photos": [{"width": 984, "height": 985, "html_attributions": ["<a href=\"https://maps.google.com/maps/contrib/110279808588468038448/photos\">Peckerwood Garden Conservation Foundation</a>"], "photo_reference": "CoQBdwAAAKdKwfjtWG8hgwNRwR-SgH_xg7wiATDfzIAeo_APLJaZK8eu8Zv4hbG1XRsJ5SnE5Dkg2AHDFzf1Iq10WX90tlmRbvVwJGNZ3eY9fDdI9m6U-HxuxCsZerPC4AWZaqlqGXTFEhfFjdvDr_EIWh7T8ou2xqYjlJ-wxpbEh19R1v1oEhBdq6pZRva_YC9bd550-WXgGhQUk2vUhUdCm0J-6hwDmt74BXJZ8w"}], "types": ["park", "point_of_interest", "establishment"], "reference": "CmRRAAAAPbizo5jfxbRiHXNntZpwu4sMP7N8omvrBkQGWfY_h7QzLErJX8VGgcJPNX-Thjw1v_L-SnmeKrHZYpcdrp6jCH6_mJXzfJSQoh1ZGeJnmnvPfy8x2zGiuT8NHNaVY_Q9EhA5TRWA2HAF_1BxjO2u-dx6GhR7HTQnX2XdQATZmmUR9ZBy1bWoqA", "name": "Peckerwood Garden Conservation Foundation", "rating": "NA", "id": "e618a4c618cd67ce4f5fdc165f640220ab3b53b2", "job_title": "Gullett-%26-Associates", "place_id": "ChIJmUR7pvHKRoYRIIl0o73bPGE", "address": "20559 Fm 359 Rd, Pine Island, TX 77445, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.64386449999999, 29.7515036], "type": "Point"}, "properties": {"photos": [], "types": ["point_of_interest", "establishment"], "reference": "CmRRAAAASl09-2ZzJEW5tR1dLhW5G4vtjMQlXUv-t9-a210b0yJt3aGIGRpKet3o4kjswKdX4FD6QEE8sBjSH56E3QA3atx-8Wpp5C_W7LSMBmNhK-TobTmWli4CoLT6KO1AZ2-7EhDr321XG0JOBmFI6uQWjNSWGhTKSgiUOjwV3viISIy40x4kINwdKw", "name": "H2O Conservation Technology", "rating": "NA", "id": "30c07988ef8dfc62dac712b9d587daa4a36f2539", "job_title": "Gullett-%26-Associates", "place_id": "ChIJIWZRKeHKQIYRXxta3wOMGGc", "address": "1725 Hwy 6, Houston, TX 77077, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.5705632, 29.7714443], "type": "Point"}, "properties": {"photos": [{"width": 3024, "height": 4032, "html_attributions": ["<a href=\"https://maps.google.com/maps/contrib/108143329814504597326/photos\">State from Jake farm</a>"], "photo_reference": "CoQBdwAAACvR6Flo8nIkbEWeceP7LoYLt4JrxkvfeQ6jWxXRUn9SsiF0QwtLpfY1gQ5vpZEelXPnsDr1I1yKa52FYa5WF2bo8vhHfH3bd1waGIOPA3nPRZxYnXuQ7ALZ8OEsSakh8RmNmrIObNLEc7LVuI_rlN7JUqkrWBLWNIMt0UvMMc1TEhAbi3HSNprDMUHS_Vpfh7fQGhQ9Cgt5q5ZMUZJCedvjhNdgBzHfbg"}], "types": ["park", "point_of_interest", "establishment"], "reference": "CmRSAAAAY4sSvfGsThG7OAK8Pn6flRiTK9mEeFJqdDV3qTEdV3wbr-mwmLEVJfsbCcwr3zZhoiQG30y-fJ0qldUVJvHIVf5pkjvAdNRw5Rw4bmv4RszUFEYfpbKr9xa_wrrNBw_EEhAZinpECKq3ej3bwCzjzdnTGhS2eJ5uQfK4D8i0nHPSVJEUwULV6w", "name": "Houston Audubon Society", "rating": 5, "id": "050a5458d86bdd1cee7b09678bd6256d0a20a73e", "job_title": "Gullett-%26-Associates", "place_id": "ChIJlQOxwVDbQIYR2uX_TZl0TYc", "address": "440 Wilchester Blvd, Houston, TX 77079, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.56820189999999, 29.770778], "type": "Point"}, "properties": {"photos": [{"width": 1800, "height": 1200, "html_attributions": ["<a href=\"https://maps.google.com/maps/contrib/108765250995932379967/photos\">Audubon Docent Guild</a>"], "photo_reference": "CoQBdwAAAOtKaaU3Lu64tqZiqEiVYV68oYi6e64SjoZpOdWXWbMC-6EoPFd_DCqbiR4DlHXJSAw7GJbtVoNS261lesG_73euiKq3ypNQsdzAERCQ5qLKti5gAljIsYs4y7Fy6PKmHC-y6zCg5M6Y6EfDf4285jPgleSwd7tDV0g4Uu0lYTJHEhC1WMxKRSU58eQX-RvIKT5vGhR9C0Y6rh2w0zm_GQO2Lmq_-DQ9-A"}], "types": ["park", "point_of_interest", "establishment"], "reference": "CmRSAAAAovKou53a_7MqVp97zcWus9ZuYgwBq2djnNO4tbUdxQBjijzwbZtRFsckvMR_dly9IH5lWGJd6L7q7E909K4lxINBnROE-Uwagc2y0WkCsd11nZX1iRalw1kntrD0jKRsEhBUrSMaElsOU0OkEE3gVD6BGhTBqhZiet7KvijLtsr_-yQWaNX9Hw", "name": "Audubon Docent Guild", "rating": 5, "id": "7ddd5daf76cc4979e2ba6b062322d1c77d5d1c07", "job_title": "Gullett-%26-Associates", "place_id": "ChIJI9XyNFHbQIYRtwHb8EtTpeU", "address": "440 Wilchester Blvd, Houston, TX 77079, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.44932349999999, 29.7803218], "type": "Point"}, "properties": {"photos": [], "types": ["point_of_interest", "establishment"], "reference": "CmRSAAAA-AxZ5ETPVptHynJ3cVPfCv8aoF8WfyhsjK_HErxb799KctwFC4R_O6xOmOOBi8-1HrPE3VHj5jLYlqiP5efvRFnAUxGgwPTGsUQx4R4RuQcBIrStBuopdY2C06A-iuUgEhBKq6W0vKPYORox5bPOri41GhTJvZR0sHQPCqHwfSTL4CKshi5ZxA", "name": "Coastal Conservation Association-Tx", "rating": 3, "id": "7258b034e119f31e82320bca6e72781ee9f79d75", "job_title": "3q-Services-Pro", "place_id": "ChIJcekacM_GQIYRPzL13cgQrPk", "address": "6919 Portwest Dr #100, Houston, TX 77024, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.47039, 29.655454], "type": "Point"}, "properties": {"photos": [{"width": 5312, "height": 2988, "html_attributions": ["<a href=\"https://maps.google.com/maps/contrib/101184977609161362375/photos\">aug4</a>"], "photo_reference": "CoQBdwAAAN6gw_8GEY7SluhAvfSZANsiSip9kdJW9-gc-gVKsy4EuD1yE6Np2xw6ypEZXubSKmFrpftjFlXJqcbOXd36cwiX-UZyXNvueYlXPxsBeJ7hoQztgvEm3UBhyrP1zn9jCMNPbhHLyP6Ha9nrwr0FVhXShgL2aC81UzgmSwFIBKceEhAAicfEY-7Rxs9lWG56XoU1GhTpTEFWL3gfa3rEKkzIndQcawajhQ"}], "types": ["park", "point_of_interest", "establishment"], "reference": "CmRRAAAAobqZm_ZY2vForpxGsW6qzFI-d89BA1oQzgyNqFFZH_yKvrMxl_0jqHj9hqU9_KrZKElbcp7QTPMKrbX5I0Lrk3JtuSnev_cycaM1utIzjrdBGSPp1GPq45ZNjr6afXmVEhAvH20zV8l8PRmy-pszNa11GhSjBeIorhP2KiAtqaJMgCrtZFhDag", "name": "Willow Waterhole Greenspace", "rating": 4.3, "id": "0127506e8071350c2d48f0ca56e939045297a0f4", "job_title": "3q-Services-Pro", "place_id": "ChIJR6_2zTzqQIYRsA7wExgfDWs", "address": "S Willow Dr, Houston, TX 77035, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.4003322, 29.7388505], "type": "Point"}, "properties": {"photos": [{"width": 1136, "height": 640, "html_attributions": ["<a href=\"https://maps.google.com/maps/contrib/117056878997299689379/photos\">Marisol Brown</a>"], "photo_reference": "CoQBdwAAALMGpKTtpoWAPSUVUEPz9KeiOV04PSDTvQwM7w9w6IdIRxfzOVM1DEldIsrsBQyDn9RzMMGzPCxd1lcjAG5nHJCFb-k_9PvnL2hITn1G-ycu88EsI5WD7cKmsWzs6qe9nq6t7ik9z-M5i7yYuMY6sk7333a38dK7-j7ZisUPU8C3EhCgfihXf4-v8WDOY8Fp2vyaGhTitNoon2pwYmiqjcBkqcwRpsd2hA"}], "types": ["point_of_interest", "establishment"], "reference": "CmRRAAAA2ryzchZQeOj5Y1-SKxA78jXXwmO-2X_7ud_rwPiCi6TGfk11D51o5ra_xn_845qqDVvtps9vcVynH3dxLQO6c-UBZSZAgdlDopiNbZJBESKl8hNHN1pIXh2Z6Bhp6ePLEhAlDJnAhxqI-16_3j8eK3HqGhRL0pAb3Yaqm5fDO3qvzm3MMgpwbw", "name": "Masters Fine Art Conservation", "rating": 5, "id": "a462c2eef4e22ea319485ae7b84f3d20756cbdd1", "job_title": "3q-Services-Pro", "place_id": "ChIJp8u2bZvAQIYRbosnWz6cVmY", "address": "1612 W Alabama St, Houston, TX 77006, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.3876169, 29.794149], "type": "Point"}, "properties": {"photos": [], "types": ["art_gallery", "point_of_interest", "establishment"], "reference": "CmRRAAAAk2o--76PJh32rXTzS4gi3qmQapsiO-JIvANhr0JwZvonHnstxWnQzpWwtJ-4FowNz4nq-FkVEMR_mwvBuoW7IEndljA0QfWTj-ESOsd3YzIwV1DboSl6iybJy0RH9rb9EhBKPuqTBTfxQx_ulTX-rCfZGhRu7zFR17dcMJm7xxj09RfQMURVcQ", "name": "Whitten & Proctor Fine Art Conservation", "rating": "NA", "id": "883a8c5ef35ab28e1630235ad65a6b16506a67fa", "job_title": "3q-Services-Pro", "place_id": "ChIJ8YuXE6K4QIYRn1SF1hazFEw", "address": "1236 Studewood St, Houston, TX 77008, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.3858767, 29.7300997], "type": "Point"}, "properties": {"photos": [], "types": ["point_of_interest", "establishment"], "reference": "CmRSAAAAj77D73WefDFpdUvHhMisjeQTLPeEKdcZ0sRUE0qjEJI5E6ZkrsxRtPyp5WMzdXp6PpJGypfsmj4p4dR8lBiQEI_-x8mihmUgieSDsy2n1C4y6DhgeaH5e8jotRzy1UBjEhCGp5m2TYjTGJ7CpaLvc-JvGhR_D_Y44e_LJWnbRHHJXqp5Y2pL9g", "name": "St Mark Fine Arts Conservation", "rating": 5, "id": "ea2d4bac6d74716b33f456dff3aae0cc0b43cca3", "job_title": "3q-Services-Pro", "place_id": "ChIJKbDEoXm_QIYRcRFBlp0dE8A", "address": "4901 Main St, Houston, TX 77002, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.483218, 29.7482286], "type": "Point"}, "properties": {"photos": [], "types": ["point_of_interest", "establishment"], "reference": "CmRRAAAAHcZGQsLsH6n9TXN9Sb49B6BPxBsfeFpq3PZ_YopRhSYcFox6Ra2vpzdr34gk0_pAGtB_Mvb8Y4ZgAwkNyJhZBuIPeyXUYrpNdXHt8B3laebfpl-hzOkaZnqOypWF42GNEhC9ZBJoQTr93hrG_xyM8gZJGhSZ_km-5ZcX6XfTa15gHTnRre-Iag", "name": "The Nature Conservancy", "rating": "NA", "id": "90af6fb9fb926dde9f7103577cebc4150bbb1dec", "job_title": "3q-Services-Pro", "place_id": "ChIJq-m4EX3AQIYRJkn4Lhccp2E", "address": "1800 Augusta Dr #240, Houston, TX 77057, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.42318089999999, 29.7345943], "type": "Point"}, "properties": {"photos": [{"width": 750, "height": 437, "html_attributions": ["<a href=\"https://maps.google.com/maps/contrib/106788706324997826205/photos\">Erika</a>"], "photo_reference": "CoQBdwAAACrvSRNK6vpvzf0XGBvNPCxAERkSq0m2ihDHzcG1kFMLQDJS6ptVb3ej9CIcoDGv_vQ3OFkdKJ0ym2zjOalKI-quxsXJQVdbdXIOGgLwkfSoqGEoglFwwP-VddY8tRuhdbrdJRovr7KSI8tLehOUGAyp9Tk9fngOZp8nOawKghOaEhAQDcmyzcqPLxiuuLMml4o1GhSKFLGtkQ5OJHwl-Cc4IJYPHlLpCQ"}], "types": ["point_of_interest", "establishment"], "reference": "CmRRAAAAE0vcI1Nz8XibcnCTvuF_jVvEcBWJfsLz9nd3O65y1oZQF-skalFlRB76pG--RIRY5u_6IcjdC23CxvxuqgUid2MpvOr_LOlxtdxPy9p0G2fPxHTjFv0pfSbnN2pXXGHREhDnNoIicmxrrsMkrUkOTWx3GhRffqFpFWsdQufMspcuw_nyHOBkaQ", "name": "Student Conservation Association", "rating": "NA", "id": "1c5ea7722fc0d99e9f7dfca55f5d9078224d51d3", "job_title": "3q-Services-Pro", "place_id": "ChIJQcqBXfDAQIYRErawO-goGj4", "address": "2990 Richmond Ave Suite #400, Houston, TX 77098, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-96.038102, 30.055621], "type": "Point"}, "properties": {"photos": [{"width": 984, "height": 985, "html_attributions": ["<a href=\"https://maps.google.com/maps/contrib/110279808588468038448/photos\">Peckerwood Garden Conservation Foundation</a>"], "photo_reference": "CoQBdwAAAA9bPnWzsFuNwxtHJOpzJSALO51wAyMk2CK41awsVvlZeZ1vBdAHjvjL4C7OlBYSdbq2Z-XulsU-wHNoUj-c99p2nwVs6EgHEn-YfMnclYUTAMIwjr8qpTFF5futQG-Bu8VI_3gjEkpJSVsEI7uf-8swkbFlmYEMdAQVUNXkbKUtEhDl2b3uzk19FSlbpXDYsdiRGhQAWvkjkJIAoXQGYbqkrD2FrJe3-A"}], "types": ["park", "point_of_interest", "establishment"], "reference": "CmRRAAAAjDqrmcBVZdWgwoQTUD3AC_KwtUQs4WADf8NMLJuQ846flr-WZdg7fNKpb-Fhyf55svkujKHfMDjurnTOBw02k3VZiX0WaRDwviIbwGjedTqw2xk_2FVyLivWxV1Z4viNEhAaq0D7AGiD_PguvXV7JpJ6GhQaqdED3sAa2KPdkH1oW82vsM2Mrw", "name": "Peckerwood Garden Conservation Foundation", "rating": "NA", "id": "e618a4c618cd67ce4f5fdc165f640220ab3b53b2", "job_title": "3q-Services-Pro", "place_id": "ChIJmUR7pvHKRoYRIIl0o73bPGE", "address": "20559 Fm 359 Rd, Pine Island, TX 77445, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.64386449999999, 29.7515036], "type": "Point"}, "properties": {"photos": [], "types": ["point_of_interest", "establishment"], "reference": "CmRRAAAAOlm-7kBzmhO6kPQM4JAGnLZUCvmFgAifTrfJ3YA8LbpRZi56wPs1qEgg-E1C3he7RkwTCAPXeAjdHQDby902TX284DIaniLSK9L-RX-XVfXtfsr23wHymrISwAKnGtpTEhDnC2KjTFYX38Xzl4dMYWJeGhTgDIVG3V8ZGqA2NDvwGD6G85HoFg", "name": "H2O Conservation Technology", "rating": "NA", "id": "30c07988ef8dfc62dac712b9d587daa4a36f2539", "job_title": "3q-Services-Pro", "place_id": "ChIJIWZRKeHKQIYRXxta3wOMGGc", "address": "1725 Hwy 6, Houston, TX 77077, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.5705632, 29.7714443], "type": "Point"}, "properties": {"photos": [{"width": 3024, "height": 4032, "html_attributions": ["<a href=\"https://maps.google.com/maps/contrib/108143329814504597326/photos\">State from Jake farm</a>"], "photo_reference": "CoQBdwAAAFwg9GzUt_wfulTyZSl9n3wAkd9nBnaiC-xdw0XY92tJQJU4pA_qG0fxLDpR8Ywhqr-Upfs0GD3P6u104dNYH0VnVdjJLbks38T4WhJwlP4ETWOuHJYSNU04TqpW5DMCJEc8rjNf3sRJ22LhLG4o86BX0C-FW13TmMPLKgg3U5MEEhDR1k1XGDPtjK1q_-A-0LJ-GhT7ENFXdPgSzAjKdAdci-cWSmHKcA"}], "types": ["park", "point_of_interest", "establishment"], "reference": "CmRSAAAANkb8saT90JuO491OjO-jatMsyeDhQIHNceIlNpVNy3uAKNiOil4rzJoehhfW8KWpNK5DoSMqbumWNWtdYET3wDVkfelgXeyK8zJpAJfwZCVpBE0Bx4dUTr-TV29J7KcxEhDC9_NY0z2aegcUhirFpEmoGhT0YOphWsO9iqNEfUHL9syooRE9pg", "name": "Houston Audubon Society", "rating": 5, "id": "050a5458d86bdd1cee7b09678bd6256d0a20a73e", "job_title": "3q-Services-Pro", "place_id": "ChIJlQOxwVDbQIYR2uX_TZl0TYc", "address": "440 Wilchester Blvd, Houston, TX 77079, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.56820189999999, 29.770778], "type": "Point"}, "properties": {"photos": [{"width": 1800, "height": 1200, "html_attributions": ["<a href=\"https://maps.google.com/maps/contrib/108765250995932379967/photos\">Audubon Docent Guild</a>"], "photo_reference": "CoQBdwAAALZZr9rsNKGGA9NHvUzuLISGxSGG2QSa8lvsRR1oIPbeLQLBHwhUbE1y90EPI2HNE2bcq4BMwYzT4AHyS5dev9Zw7kiIsEZBKFemVphoDjIm4wrTL2CXVIOm3JWWrQCR-Kh5RByxT8a7i4uWq-4tA-Ps2tf9xAD8hfikPOrly1qGEhCWHZ3N6-uPAWxSjy46yWC3GhS5WxzOW31tuqR3RLVMZMEzscwbHA"}], "types": ["park", "point_of_interest", "establishment"], "reference": "CmRSAAAAceB1oK3uJr7Z_dCxkGQkxpPCKTqTHGvZiJyuncExb0ZWGgO1nPp_ZB5Y7oPjNIeo7Iz-T0LHpZLNNnd59GYkavYoWCo0Gtq4kWOccAaZDCeG6hYa-rpmZHPH926P_iFYEhCJPcRhpoWV2s4E8fargzxLGhSTj7tDL0aoslKTokTp8NxpACSKKQ", "name": "Audubon Docent Guild", "rating": 5, "id": "7ddd5daf76cc4979e2ba6b062322d1c77d5d1c07", "job_title": "3q-Services-Pro", "place_id": "ChIJI9XyNFHbQIYRtwHb8EtTpeU", "address": "440 Wilchester Blvd, Houston, TX 77079, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.44932349999999, 29.7803218], "type": "Point"}, "properties": {"photos": [], "types": ["point_of_interest", "establishment"], "reference": "CmRSAAAAN1rQHxwPUBGi5FzDKsk9gSzZK6LD4Wz_ttPkG7XxGgW-Jw-F329viNMpW8S6xR1bN6Nqh2HIVZcnkXK2u5g_TTzNkjEy7hnU16zoJvJ4ZN-LwMTYJvP16kBpr7tgbTovEhB0lRLzCorwxgzXWMWICxDGGhTSxSLd0Wl8tc6epa5hLZE4q1Yt9Q", "name": "Coastal Conservation Association-Tx", "rating": 3, "id": "7258b034e119f31e82320bca6e72781ee9f79d75", "job_title": "Watco-Companies", "place_id": "ChIJcekacM_GQIYRPzL13cgQrPk", "address": "6919 Portwest Dr #100, Houston, TX 77024, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.47039, 29.655454], "type": "Point"}, "properties": {"photos": [{"width": 5312, "height": 2988, "html_attributions": ["<a href=\"https://maps.google.com/maps/contrib/101184977609161362375/photos\">aug4</a>"], "photo_reference": "CoQBdwAAANwvlfMN-TmTUIxBIWVjb9MWM5MWrYUW_YKYMQxqKdadMNwyWiBWTW3ECyLwnENIQDsnE9Bhxj_fQisZ6Iorb7DQqqhyN9jxOnJHjfciUfzdXCFigLbAhtLyYhaUaT4rlv157VYipDKIQX6zrGuN2tRsnWBzTpWn9Fvtzv3NIuvQEhCBlKAXWjCJW6FSm0UuOSXxGhQrRfwY4wsNo8u9ahOkFlJ2h3LEVw"}], "types": ["park", "point_of_interest", "establishment"], "reference": "CmRRAAAAToWyvaClR1piZCOyIkEjbyuk-FXDrgGVoEUkbJgihtgWQ0agamgUl7NwIrRgh3eTuuivf5e8O2HhhswmlsxLJrmaoJAtZvLFx0k7Lgvk8gt9lETHIOT3LOBctS0l_IY3EhDBs2gjAG0N9ZDk7F3CFuB_GhSykWst3rhXQsXh4QqsoGlg4cpKSA", "name": "Willow Waterhole Greenspace", "rating": 4.3, "id": "0127506e8071350c2d48f0ca56e939045297a0f4", "job_title": "Watco-Companies", "place_id": "ChIJR6_2zTzqQIYRsA7wExgfDWs", "address": "S Willow Dr, Houston, TX 77035, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.4003322, 29.7388505], "type": "Point"}, "properties": {"photos": [{"width": 1136, "height": 640, "html_attributions": ["<a href=\"https://maps.google.com/maps/contrib/117056878997299689379/photos\">Marisol Brown</a>"], "photo_reference": "CoQBdwAAAKpTrAS9TLoHoqhsqnm-Pd7sUYkNSYjvDvFI05z6PSy2Yg3yoyLFKNP2KQW-XRfGHoQFKJVkwuqm-xjqp3-vxgRTBLjoJj1pvW26pzdKBAGqHpsuAusOerzEEezboux_8U6gJV2ZUUWtZpKZkeG_5KtTKYEjbu2OSjdRgWVGssK8EhAkTmWEj1B7zQNdkeweJpzLGhQceIsdP2R8U90Vq-I8s9RZBbRUuQ"}], "types": ["point_of_interest", "establishment"], "reference": "CmRRAAAAU0CGAAn-bpHi-eGSvfkmf0MUPwB7b58quXjWaS-Wfx4fIdgGdHjINvzgwZTLjb5F04IhzbX4_jybmnlG7UdA6suSI44xr6Ym2Nt_Mf-Jugiksz-pkc6S9b1uJQxVi9onEhBVtLppJG3H3XrQqH6HnW2kGhQaCvkZ58MkVpdH45JyDOoxzZeeaA", "name": "Masters Fine Art Conservation", "rating": 5, "id": "a462c2eef4e22ea319485ae7b84f3d20756cbdd1", "job_title": "Watco-Companies", "place_id": "ChIJp8u2bZvAQIYRbosnWz6cVmY", "address": "1612 W Alabama St, Houston, TX 77006, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.3876169, 29.794149], "type": "Point"}, "properties": {"photos": [], "types": ["art_gallery", "point_of_interest", "establishment"], "reference": "CmRRAAAAwG-b9oVuIY75d9mQtMuPghbLMliucETuzfqICV-sM2VWGZhI7_zGYjrr_8PoVX0XkZfQzkhgCxMXmRxTrK_7mrrESgTJRdFxSZkKzHMf_GyVXmILXgYng6YeKtmobMxNEhCz12MNK9INDYxGufc7JyEOGhQEtpgRBuwNwghr7CTQDi_YJBnpZQ", "name": "Whitten & Proctor Fine Art Conservation", "rating": "NA", "id": "883a8c5ef35ab28e1630235ad65a6b16506a67fa", "job_title": "Watco-Companies", "place_id": "ChIJ8YuXE6K4QIYRn1SF1hazFEw", "address": "1236 Studewood St, Houston, TX 77008, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.3858767, 29.7300997], "type": "Point"}, "properties": {"photos": [], "types": ["point_of_interest", "establishment"], "reference": "CmRSAAAAwBJz-X0U1uSEQgwomS0RHYnybdzje4o7f7HmFL_VAGlTQSRvlWOOuxabiFSK9jpT0Y6hzP36oQu6bCXX6gVQyGYXmQxm4unUTuXf8iHa_NS7Lh_AY0FDx8RdgXqcDiZ4EhCFNb7oWdwQ7geyY8-9038OGhRo2Z2CNA5xOZYPQTXDt5UvG2uGRA", "name": "St Mark Fine Arts Conservation", "rating": 5, "id": "ea2d4bac6d74716b33f456dff3aae0cc0b43cca3", "job_title": "Watco-Companies", "place_id": "ChIJKbDEoXm_QIYRcRFBlp0dE8A", "address": "4901 Main St, Houston, TX 77002, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.483218, 29.7482286], "type": "Point"}, "properties": {"photos": [], "types": ["point_of_interest", "establishment"], "reference": "CmRRAAAAZA1NS6Fbk5-Jm0F2wKT2lzeRRzVbIQ43XEyukPOW1OA2r5Hbes-atFMaQ-gBzXct3mP54UMW-IsbgEISsUPNlt5HCL9lM4Ctm7cX6ky2kSB-_paCNH0-oD33L3x_zsZnEhBP0T8Z0Se7CfH5OEHNwx_tGhRVoqdHtFUkLiUb0Ry0SUtzINstuw", "name": "The Nature Conservancy", "rating": "NA", "id": "90af6fb9fb926dde9f7103577cebc4150bbb1dec", "job_title": "Watco-Companies", "place_id": "ChIJq-m4EX3AQIYRJkn4Lhccp2E", "address": "1800 Augusta Dr #240, Houston, TX 77057, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.42318089999999, 29.7345943], "type": "Point"}, "properties": {"photos": [{"width": 750, "height": 437, "html_attributions": ["<a href=\"https://maps.google.com/maps/contrib/106788706324997826205/photos\">Erika</a>"], "photo_reference": "CoQBdwAAANwfxToA0p1ZegEqNpEZSks_zZHPOV7MiXitdBW7UCBX7_RfLyZgeH_lzY3dCXynuNSakqtNEg-rD74htyp7dObkqc8j8sU5_WzCQen81Wex4cppUzY05-qvG0rkXcimFZXTxBDZE5EYkOAJSXPEQ8VuaywBmhzX1MhDOYX55n-3EhAHycYODkZYCd6W2YwaDpWRGhRQtYtBQUmDsdJv8HAZ-SSM4kkPBw"}], "types": ["point_of_interest", "establishment"], "reference": "CmRRAAAA3chfUAfUcSaC6vrbA_FjIAL94mLvFRiq5SRq2S1N8iXk_AMXwxfz650mBYLeRoSBhfg1x0xadevuLIXoflBmxdz8LqorcJO0P7mhKAxJ86zYrctE9_KLOwOqq4a7tdULEhCVYoJR_YkEULi_x0-JJQY9GhTuQ2V9zWIAeF1JD2ekjsG9j6kBUQ", "name": "Student Conservation Association", "rating": "NA", "id": "1c5ea7722fc0d99e9f7dfca55f5d9078224d51d3", "job_title": "Watco-Companies", "place_id": "ChIJQcqBXfDAQIYRErawO-goGj4", "address": "2990 Richmond Ave Suite #400, Houston, TX 77098, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-96.038102, 30.055621], "type": "Point"}, "properties": {"photos": [{"width": 984, "height": 985, "html_attributions": ["<a href=\"https://maps.google.com/maps/contrib/110279808588468038448/photos\">Peckerwood Garden Conservation Foundation</a>"], "photo_reference": "CoQBdwAAABATKqGX9ZiR6RnaFN3azcgzLARR9Qf7bnQ7b3zsb_G40PDUjDfI-pQo5K-9EcDWYVI5B1OKZCRaNRKTSH1Bxjt06L0uTPzcL0FXPCKMwCH0l6CNtXqp5vK3Z_c8FAXpKNsNxRymmSxp5q05-d5h0RE-7nc8lEG7vrRQNd1OPkDIEhDccZSTZxBAPL7r9BNyyMJGGhQc5Eej9p8I1-zE3iN2zDNGGWU0CA"}], "types": ["park", "point_of_interest", "establishment"], "reference": "CmRRAAAA8vMsfsVZmQHcVM1ityYtsQDDRf6XlIGuroRIb4MAHiftRXtY9yI0avHD9ea8BTEZ8_x5pO7hkxjyhRBZm5oxq7RG5DkYkAEyXsAbD835dtkmhPW7DNx3JJB3ZmJKgUzxEhAY-J8NGAB90iELLm4Th7uCGhQNBqHrouLgav2SJxGqEAHyeD4BqA", "name": "Peckerwood Garden Conservation Foundation", "rating": "NA", "id": "e618a4c618cd67ce4f5fdc165f640220ab3b53b2", "job_title": "Watco-Companies", "place_id": "ChIJmUR7pvHKRoYRIIl0o73bPGE", "address": "20559 Fm 359 Rd, Pine Island, TX 77445, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.64386449999999, 29.7515036], "type": "Point"}, "properties": {"photos": [], "types": ["point_of_interest", "establishment"], "reference": "CmRRAAAAJ7LllklVHpNr8uTXflySqz8-h8om_-_iO1fnzLmkwJKBvi9EOpK8OPR52jiu8BEikU1aGWzLA1dvCq3I5VQ4yiKMiJLqmy4MjV8e_VD2Q3SpvTiPFvhq4oQPdYuYV3FAEhDFqhzaReZE9Cs1EVkRae4KGhRvdzheXJ7_CroRJBPpLuFqTo4Otg", "name": "H2O Conservation Technology", "rating": "NA", "id": "30c07988ef8dfc62dac712b9d587daa4a36f2539", "job_title": "Watco-Companies", "place_id": "ChIJIWZRKeHKQIYRXxta3wOMGGc", "address": "1725 Hwy 6, Houston, TX 77077, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.5705632, 29.7714443], "type": "Point"}, "properties": {"photos": [{"width": 3024, "height": 4032, "html_attributions": ["<a href=\"https://maps.google.com/maps/contrib/108143329814504597326/photos\">State from Jake farm</a>"], "photo_reference": "CoQBdwAAAEWAqoBLSbIR25bA85uiL5qabYzDS6IL2J6-lqXUgOkuR_17h0GQUPJcSlwZmKpFz7m7lGhiAXmtI_10XxiiB-7zjMfzjzis_2UCRJDopBNoRKHCVkL8vKYFWamJ4eqqcQtH8wk8Astc23ULmOFcShSRf4Ue3dqbdB4MaRSODKyNEhBUuoLHryC4hb2xS-7K7QXmGhSoCGEoZWkhq6Kv0Sdn4yaiZU-B_A"}], "types": ["park", "point_of_interest", "establishment"], "reference": "CmRSAAAATX70qlo4FXXS6ncj8bSrAONhwvaguZGSHqHihCYurSdGWUShxpk90NTHCxW3jzZzdMxubuX3YtJZdM39leIoTT2_NtCZe41fNyoYEAR61sv5nWCSLHynfzmvNUCMIcfkEhB_Jo1dHanAl3OGMmAb8AEdGhTb5H8wy0E4nD6TlqOQAuAdABkj2w", "name": "Houston Audubon Society", "rating": 5, "id": "050a5458d86bdd1cee7b09678bd6256d0a20a73e", "job_title": "Watco-Companies", "place_id": "ChIJlQOxwVDbQIYR2uX_TZl0TYc", "address": "440 Wilchester Blvd, Houston, TX 77079, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.56820189999999, 29.770778], "type": "Point"}, "properties": {"photos": [{"width": 1800, "height": 1200, "html_attributions": ["<a href=\"https://maps.google.com/maps/contrib/108765250995932379967/photos\">Audubon Docent Guild</a>"], "photo_reference": "CoQBdwAAAF13bm4ImZSCoTfgh4bjnV8zNWX17MLc0akwOC1ewDcuyskbe4xP2QeCpef3pr6iF6g7558GlWInNns1dInl0Vyd3rLHLLvEUCeFRYcPV9Mox2QXdwHvcWVypwQZ0l1QTrodYfy-MYAgglVdVqe2DXeEXN3KKBSDcC8WRIonNZzTEhAMNfHzKw3PxkERC92Dn8v7GhQrSZ4GH30vcU1ypNmWZsXZH-Slsw"}], "types": ["park", "point_of_interest", "establishment"], "reference": "CmRSAAAA-lQJ0lUY_MGfu--35LazvtzEYo8zw6u7mNerbvjUYKuhI3l_AauIt1qU9HCwJEyUyED61F7QrjhFIzxE7Wkwaz4xiSqF9sCjDgZuo2debZnm6DXtHwOLVmdvg9Q_DUwKEhAnOsahfGQ9F8DCTS-_05_XGhR2KSr0xYrn1nvOWKGMjY_0cJWJbg", "name": "Audubon Docent Guild", "rating": 5, "id": "7ddd5daf76cc4979e2ba6b062322d1c77d5d1c07", "job_title": "Watco-Companies", "place_id": "ChIJI9XyNFHbQIYRtwHb8EtTpeU", "address": "440 Wilchester Blvd, Houston, TX 77079, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.44932349999999, 29.7803218], "type": "Point"}, "properties": {"photos": [], "types": ["point_of_interest", "establishment"], "reference": "CmRSAAAAMjvcdvV3fCl-qmuu2HkK3JbqA_PVQP9U7EKQNtu4H7UUI0ytiTLKmJL_ws82OEHyoc8eL28M_Nuf_bAZtc2WiA3GttQ1juXF5hgJ5qiTWFeJGCSE2TodaFaUHbiSSp3HEhCK0a-qy655SV2Bz6WiCe9XGhQsDHv7-7apB0vMsG5N9leKhNlYHg", "name": "Coastal Conservation Association-Tx", "rating": 3, "id": "7258b034e119f31e82320bca6e72781ee9f79d75", "job_title": "Nextera-Energy", "place_id": "ChIJcekacM_GQIYRPzL13cgQrPk", "address": "6919 Portwest Dr #100, Houston, TX 77024, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.47039, 29.655454], "type": "Point"}, "properties": {"photos": [{"width": 5312, "height": 2988, "html_attributions": ["<a href=\"https://maps.google.com/maps/contrib/101184977609161362375/photos\">aug4</a>"], "photo_reference": "CoQBdwAAAPMJqLGGwWnmkanhOV10_mU3J9HLqIzUSjxRlOSjeJtox0HA2Y4XnZqLxFVC7Ie2rwZw9DSSGUUzkUyhSPMBoM0qQfcOrNz4S6fFXM_yFKvEAli4xvQwHLZ0NuP-2JX2hIY7FjOC-UVeTKo8P3QZvfHBBAJfLLunjXBEIIyiH1F7EhDffN9YYNgI7Wyl9ifPTWkLGhTeeS-BvgfqpkBTR0OpZtRZxn0z1Q"}], "types": ["park", "point_of_interest", "establishment"], "reference": "CmRRAAAAc6YByEuw17YB3Lz2jUOy5191NrGTpEwrZzJDZv1wiXdTO3yp9-Sk3tPgWQN4A7PukwtomARqzfYRXwgktyN_XqlRGFQEw6V1gJdWQ5VOz8TcWZmP9iHwufex4Uf_1Si5EhCCYnrePJFatXyU-kt-2ZrXGhTcIZeKcqzc3w59QKNtCVdhwbvyhg", "name": "Willow Waterhole Greenspace", "rating": 4.3, "id": "0127506e8071350c2d48f0ca56e939045297a0f4", "job_title": "Nextera-Energy", "place_id": "ChIJR6_2zTzqQIYRsA7wExgfDWs", "address": "S Willow Dr, Houston, TX 77035, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.4003322, 29.7388505], "type": "Point"}, "properties": {"photos": [{"width": 1136, "height": 640, "html_attributions": ["<a href=\"https://maps.google.com/maps/contrib/117056878997299689379/photos\">Marisol Brown</a>"], "photo_reference": "CoQBdwAAAATp2EDK6sMSoJBzXeXKw8l1GJXkdbUyGNMe6cTiwlt5JYgv38TMyfaGkoRhGSajCVR_dzcqr8opXdrB4rEAHIg_aSA2yiBesJbDeWyR_F-11ZT7gonVpDA_uoUPDwK19ruvXv7KhP4KYsVN1mnAkBG_bExmdISUSBljC2Ewyi1EEhCTZswUP1kt0kv0in7IwG48GhSaMO-eVikckS1anlQ_Bh_ehAWNgg"}], "types": ["point_of_interest", "establishment"], "reference": "CmRRAAAAmoAXaYm4zgFwCsk2LdATf-rWQX40AGE-vJPPfufVgZpYRirNM39yFu9vrCKmSUBV5x_7cSfMkB_Y8ah2gAYYWrp9NHWAyNKirKIwJrY8e_ChmQdlhKs0AYd7wcgiECiQEhDFtJuPD1suJeqETrkC79jyGhT0LJMEVAQDb6qvsc2dFfNJXkERKQ", "name": "Masters Fine Art Conservation", "rating": 5, "id": "a462c2eef4e22ea319485ae7b84f3d20756cbdd1", "job_title": "Nextera-Energy", "place_id": "ChIJp8u2bZvAQIYRbosnWz6cVmY", "address": "1612 W Alabama St, Houston, TX 77006, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.3876169, 29.794149], "type": "Point"}, "properties": {"photos": [], "types": ["art_gallery", "point_of_interest", "establishment"], "reference": "CmRRAAAAMlOqZnnFeyeMDDVUyL1qFEV8MJfW7YVooqGIj1Rl1VrfQsV3Gl3t7ZE5_ahDf4d_1zrFRQDy_z5z6chFQnMmNcSzOG9-p1HwUhXNLGijHl4PK2b5Jk7PR8KUBs-duvW7EhBg4-mcX3Sf99zrGoZZN0wLGhTERlNPZkjfGvsp-quByz_3JGs5JA", "name": "Whitten & Proctor Fine Art Conservation", "rating": "NA", "id": "883a8c5ef35ab28e1630235ad65a6b16506a67fa", "job_title": "Nextera-Energy", "place_id": "ChIJ8YuXE6K4QIYRn1SF1hazFEw", "address": "1236 Studewood St, Houston, TX 77008, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.3858767, 29.7300997], "type": "Point"}, "properties": {"photos": [], "types": ["point_of_interest", "establishment"], "reference": "CmRSAAAAWGE0wHFqgWVNi-CEfQ5nHQNo2DWObmN2YBd-t6tlWhDjj4_8Sej4qeXHKc2Kmm6qG59fc9uW2egU_pI_npZAx9pyoUcP_MO3dAk2FyQTREJWzK2irFy1eCuaZ4HUaLSxEhBLVTPtZVINz0DWh9iKtOLHGhTmWcuv2bV-XMEpCrYrfUc8jE8w8A", "name": "St Mark Fine Arts Conservation", "rating": 5, "id": "ea2d4bac6d74716b33f456dff3aae0cc0b43cca3", "job_title": "Nextera-Energy", "place_id": "ChIJKbDEoXm_QIYRcRFBlp0dE8A", "address": "4901 Main St, Houston, TX 77002, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.483218, 29.7482286], "type": "Point"}, "properties": {"photos": [], "types": ["point_of_interest", "establishment"], "reference": "CmRRAAAA7sP6qUifyJPMKpxu0dAJ0jqW7fkWT-MCFOEY7ZUwCzOUaPDopigytlwx0psKGmUmuGdmwQNOw_lxeT4VVlhDesNNZL0BRVb2Oi8jTWrmbVTarlR7WqXMlz2S_4sOB__6EhBRMtVxlh_Q6xpJcCSZ6U16GhSSv_7Z8-IYBwlCDu3bvE6kq_WD-g", "name": "The Nature Conservancy", "rating": "NA", "id": "90af6fb9fb926dde9f7103577cebc4150bbb1dec", "job_title": "Nextera-Energy", "place_id": "ChIJq-m4EX3AQIYRJkn4Lhccp2E", "address": "1800 Augusta Dr #240, Houston, TX 77057, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.42318089999999, 29.7345943], "type": "Point"}, "properties": {"photos": [{"width": 750, "height": 437, "html_attributions": ["<a href=\"https://maps.google.com/maps/contrib/106788706324997826205/photos\">Erika</a>"], "photo_reference": "CoQBdwAAAIVlMJiFDj1fBmWhaieYAWJE-PvTSs7EJidPS1iSrQByxnQILJdMpJpgxYpE4hG8HnfD-_rYpFcRtxMmF3e3P7PN52ONUkolkj1yhjY2u0OKGxhlidRUA9T1ilaueTJgkg7AR84qwPWOAKM7EK3bQgUmk9JdLn-oDPQbtCe0QppCEhDtiBGXkgSQ9cTLQmJCFgqzGhSfFDHLVw0HDBSt1TyCS3eLEiiFKg"}], "types": ["point_of_interest", "establishment"], "reference": "CmRRAAAAe26FBuTxIepeuGi-66G3C58cWH1NywM372QOFJzR4oOFX3g2ZzzjNogoHP8slmnUc9XFSFQLjTGy6jh2utF9tiKfg8MqVWgNCuA-6kWzOeSr_sTinqm2bsS_OJr7uLiYEhAvedSaQmmXlGjdgEnQZoXbGhRA1ivFngQZJGGi-X62Bvqir3sghw", "name": "Student Conservation Association", "rating": "NA", "id": "1c5ea7722fc0d99e9f7dfca55f5d9078224d51d3", "job_title": "Nextera-Energy", "place_id": "ChIJQcqBXfDAQIYRErawO-goGj4", "address": "2990 Richmond Ave Suite #400, Houston, TX 77098, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-96.038102, 30.055621], "type": "Point"}, "properties": {"photos": [{"width": 984, "height": 985, "html_attributions": ["<a href=\"https://maps.google.com/maps/contrib/110279808588468038448/photos\">Peckerwood Garden Conservation Foundation</a>"], "photo_reference": "CoQBdwAAAChFYgFW1Na7-W6lE87oG3FlM6ZiFnoW5IaMohrcWXAVpQN4qTortFZil0RE0Kk3P9F_UCY1_AqJvvqVZ8YwD8qFLvNY-XvOmCiLSm0uhWFpBbnKjKKHcDxHIYtO8yCnRYKBFn9uzbqq3i6nc6SoGLkQh1Vcii13JjQ89HX_ZukXEhDpK6Q1JC8-WKL4B7vedaytGhTnhXS9BTOIGNtQdx7KNnxrZoeabw"}], "types": ["park", "point_of_interest", "establishment"], "reference": "CmRRAAAAOiop-XPrJfgdvNdTO8GUGjAm_XCtzfTz72jON52HY9hWRflZhdg6MlLPWBya01SQUIYMNAtZQcUOJ-spcbht1D9KVqPp53RRCsUnzudu6MaNp__YiupQ988d4NSH1CirEhAXId84dbvsLBDTiIf40ILbGhRGvG_Cf4GmvuCM7vMFhqcbjpSPKQ", "name": "Peckerwood Garden Conservation Foundation", "rating": "NA", "id": "e618a4c618cd67ce4f5fdc165f640220ab3b53b2", "job_title": "Nextera-Energy", "place_id": "ChIJmUR7pvHKRoYRIIl0o73bPGE", "address": "20559 Fm 359 Rd, Pine Island, TX 77445, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.64386449999999, 29.7515036], "type": "Point"}, "properties": {"photos": [], "types": ["point_of_interest", "establishment"], "reference": "CmRRAAAAtLhjQyNH3R9M0fhMgegA7i9M6Db8jdzco1OTYPAAeXHxd9FIvKnjhqC0749Q_BqBpYXAg59BwNniSi_JuhZV1p5jaRch2JorTdTj3-XaJXXWdHT8rZw7ob0LBEoXk7vIEhBG9EotzW3yENTNZg7bHywqGhSc_8ARz9Tim7IGVPC38dz8FmKIdw", "name": "H2O Conservation Technology", "rating": "NA", "id": "30c07988ef8dfc62dac712b9d587daa4a36f2539", "job_title": "Nextera-Energy", "place_id": "ChIJIWZRKeHKQIYRXxta3wOMGGc", "address": "1725 Hwy 6, Houston, TX 77077, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.5705632, 29.7714443], "type": "Point"}, "properties": {"photos": [{"width": 3024, "height": 4032, "html_attributions": ["<a href=\"https://maps.google.com/maps/contrib/108143329814504597326/photos\">State from Jake farm</a>"], "photo_reference": "CoQBdwAAADTVvDnJHmSCdQYoborU2gdoFyZz6iYX1OT5oo-zIpoW8ACWShh9x6WotpRELepCZhk4bgjhosx2sy5NLX-iUQHaLUt1EWokfVhG_wP7jn3PitxjmfPfjVv-wqJHqVBBm9YYO2EADNiSMhe-WDyUqOfJrtC5JN_r8xB5SyPC6RhkEhB-ItztNwmN-TC5Io8Xk_f1GhTJs4Nl37kTLTF9MAhJi4nVAuSozg"}], "types": ["park", "point_of_interest", "establishment"], "reference": "CmRSAAAAnSJgsh0kIrw4EK2IKvnlezlpAtZUp15oymiysPpOijnrx4P9Fp9fJoCv0fGkUqB-W1YkPFINqcsDNgHZgpCvtfMkiFHyxWRzxfTbtpUL8eYzSW4dAI6RUgCoWMOZgYpdEhBqzlqaMbZDHAAls1nXWwNAGhTCWUZgWjz32Q5JN-Hf1_03PqTHzg", "name": "Houston Audubon Society", "rating": 5, "id": "050a5458d86bdd1cee7b09678bd6256d0a20a73e", "job_title": "Nextera-Energy", "place_id": "ChIJlQOxwVDbQIYR2uX_TZl0TYc", "address": "440 Wilchester Blvd, Houston, TX 77079, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.56820189999999, 29.770778], "type": "Point"}, "properties": {"photos": [{"width": 1800, "height": 1200, "html_attributions": ["<a href=\"https://maps.google.com/maps/contrib/108765250995932379967/photos\">Audubon Docent Guild</a>"], "photo_reference": "CoQBdwAAACFC0xJDvslNbDaZyK3qnH1yjleyS8G_R5_8mVheVibc484Wam0kFHNd4ie0IjLLCGbh8OERsDNbJ-YL-LA6-zX8A80A8ZQvOkh8myLMlK8eLx7HHKYBlDlJM2-TwANeH4OetWBIlRRdhLGpvsmnC3H66VDhhEyq-EwVIQkvHIdkEhDBW-W5T_cpd842LCUMqDLuGhQb-wFcAIefZQU9GEvj1bcAUU2_ww"}], "types": ["park", "point_of_interest", "establishment"], "reference": "CmRSAAAAVPEHHDLGcso-4Tn6ZHWuHcr73HfRMOwWuN_9OTAEK3OZLJpvr-Am1TVnMgiy7wiXRWsxY2bzjUqzffh44pIgufCjat3-wHMEPDMNalGIHX8Mqqs-iEtpOiVUCTrsgjBXEhCuOYUCLJlWkqLz-CthHEupGhRbhkq7p9YkdL1n4-N0u1nxyyMlVA", "name": "Audubon Docent Guild", "rating": 5, "id": "7ddd5daf76cc4979e2ba6b062322d1c77d5d1c07", "job_title": "Nextera-Energy", "place_id": "ChIJI9XyNFHbQIYRtwHb8EtTpeU", "address": "440 Wilchester Blvd, Houston, TX 77079, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.44932349999999, 29.7803218], "type": "Point"}, "properties": {"photos": [], "types": ["point_of_interest", "establishment"], "reference": "CmRSAAAADnbVeRAcch6ccm9jM0doEDCvVUzpZgWXNHs7bFWc0EID9eePFDUBUiANmoON3FUVJvkLXaUF5mQsgvDraw8GiKOM-xjq86xHMBSW3jt8T9j7E84vEwds46c9jqHqN27iEhCozhfAFeZA-fjfNS0DFlpgGhROgfxPAsWy57W3BI_b_SMIFwowcg", "name": "Coastal Conservation Association-Tx", "rating": 3, "id": "7258b034e119f31e82320bca6e72781ee9f79d75", "job_title": "Phillips-66", "place_id": "ChIJcekacM_GQIYRPzL13cgQrPk", "address": "6919 Portwest Dr #100, Houston, TX 77024, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.47039, 29.655454], "type": "Point"}, "properties": {"photos": [{"width": 5312, "height": 2988, "html_attributions": ["<a href=\"https://maps.google.com/maps/contrib/101184977609161362375/photos\">aug4</a>"], "photo_reference": "CoQBdwAAAC4RA8WXhu34bfbSAccajA7mMjwUXKcLhrga0wva2jE8JN6JuM5EhfeTFLvj5uw_7MIj4_iwABPmY-xR-mTwReDaUtLuw1VqbixDdLs8iUauVm8jSvN7laqByGDrkvhkl4v2PI6Z-Gk1lmUmdX_9DVXyge_7xxQ5sdqxbWfPsS0vEhAEiSZS-0KFevACdXMepuqRGhSGX4YfNl5R5slcxyfrnSQ8b1QJOA"}], "types": ["park", "point_of_interest", "establishment"], "reference": "CmRRAAAAmtjJlPnbkoA_wMNW_arU1NALpedVMV5oRHzihyvVSwkqvCBBQmtWMSDaBAfWsrh5Gtdxbj_N6C4YlGdAMZ2IBncWUn6NSI5xOswA0Dh4RLJRNzINdlCSDnibx25M2xJ7EhCvnuq7IoFGvWXNHD7UdS5lGhSsasoGhHGWVd7Pcmxab_AY48slnA", "name": "Willow Waterhole Greenspace", "rating": 4.3, "id": "0127506e8071350c2d48f0ca56e939045297a0f4", "job_title": "Phillips-66", "place_id": "ChIJR6_2zTzqQIYRsA7wExgfDWs", "address": "S Willow Dr, Houston, TX 77035, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.4003322, 29.7388505], "type": "Point"}, "properties": {"photos": [{"width": 1136, "height": 640, "html_attributions": ["<a href=\"https://maps.google.com/maps/contrib/117056878997299689379/photos\">Marisol Brown</a>"], "photo_reference": "CoQBdwAAABU_hDP4ei9Dvvml5IrG8K15gJwsPDyvS-ZIki3Dh9RK0BqA9teybioCGiHE_dOd4lPAg814tTulv69ICXCrAFy9HuepMviapYVIe3VUSPrdcQYWKHhUFfO9CGsX82y5Wz9vXyfzURzNfrocwXwXCq903max-0FdF9HVNuuzw1mhEhB8eLrUQ5a9O-WEolf4NwiTGhTuhoTOWvG5N_722khB5cBchr-JMQ"}], "types": ["point_of_interest", "establishment"], "reference": "CmRRAAAAS9GDOVmtjPTcaichSDlIe2R4pgWY1vW6P8NyQoyKd8qk06kIt_1DDhsGFt8HpKQHL6VUqOtGAVOIUGaJijT-bzqACGRIMlQDv7FwJfxErDiO-tuYuH_1qQKrX831MJH6EhC8nZ6pC8aHmS8kPvpp62SLGhSHDTY3BLVdORt_Lfn9YZbxRvMVLA", "name": "Masters Fine Art Conservation", "rating": 5, "id": "a462c2eef4e22ea319485ae7b84f3d20756cbdd1", "job_title": "Phillips-66", "place_id": "ChIJp8u2bZvAQIYRbosnWz6cVmY", "address": "1612 W Alabama St, Houston, TX 77006, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.3876169, 29.794149], "type": "Point"}, "properties": {"photos": [], "types": ["art_gallery", "point_of_interest", "establishment"], "reference": "CmRRAAAAK_auuqBscKsoB-GJLaGCofEAR_v_tq60C8BAqrbP4a4zLNXcJuHmL6AM-tVs5lxoJm1Syyh6DguHLMFwNu3MjK032Dbno8Vgbjr0BbXHxujolhmiCOG-PqC4pNA4-qsrEhBwyXa2o6X8vIiI-NjFKUB1GhQuB6VVrXITdv8SMaelW_m6X9BCog", "name": "Whitten & Proctor Fine Art Conservation", "rating": "NA", "id": "883a8c5ef35ab28e1630235ad65a6b16506a67fa", "job_title": "Phillips-66", "place_id": "ChIJ8YuXE6K4QIYRn1SF1hazFEw", "address": "1236 Studewood St, Houston, TX 77008, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.3858767, 29.7300997], "type": "Point"}, "properties": {"photos": [], "types": ["point_of_interest", "establishment"], "reference": "CmRSAAAAK3MQrKt1asfhLK4kehgZSSCPgI2n8zUlbfO1tvKfq8VYMgVo3wOyQYusYL8CpikSU86qLC503BSh-CD1SIGESYDN_xW_qgSYV-Z6l58S-Ee6y3M1ajCjzYIIc4HSHxigEhCnH4Gpm0DWGsHykBytQR27GhQVLI2NGpCuAjYAHHZ-8Yd2ydjfVA", "name": "St Mark Fine Arts Conservation", "rating": 5, "id": "ea2d4bac6d74716b33f456dff3aae0cc0b43cca3", "job_title": "Phillips-66", "place_id": "ChIJKbDEoXm_QIYRcRFBlp0dE8A", "address": "4901 Main St, Houston, TX 77002, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.483218, 29.7482286], "type": "Point"}, "properties": {"photos": [], "types": ["point_of_interest", "establishment"], "reference": "CmRRAAAAwNVXT0g_Wp7060PQNvWnJw55eO-IPuly2Vgeud8WGRMA_XuoTWyu48bb5bdMXwDcFpqRB-768yi9x1RdyNnEFTl-AgSEs8SkMC6Z_lirT4r38QQ-dxY6Gvf8oL8e_eDeEhCNGzuCHepa-BOQdOiqNUANGhQcZ8GFF8Ypa7RwuFpCuoB0x5D-mQ", "name": "The Nature Conservancy", "rating": "NA", "id": "90af6fb9fb926dde9f7103577cebc4150bbb1dec", "job_title": "Phillips-66", "place_id": "ChIJq-m4EX3AQIYRJkn4Lhccp2E", "address": "1800 Augusta Dr #240, Houston, TX 77057, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.42318089999999, 29.7345943], "type": "Point"}, "properties": {"photos": [{"width": 750, "height": 437, "html_attributions": ["<a href=\"https://maps.google.com/maps/contrib/106788706324997826205/photos\">Erika</a>"], "photo_reference": "CoQBdwAAAGX0FgQLC_tWXNmPprnLWBkUDli_wggR9PWe6BzntOKUscx1y6ORh4xq_NJFaaY-0K8JuhnEnUyz1MojTjtD6s3ih8bbsi-vnFR-g46VmIOyShK9v2YTnNFie3jMfgJv8WVg7ZGnE5X5llHEVGe5om6rqR8dP8FTVef-1aPcG1CpEhBBz3oOLMEuaRXZNF4_HIJJGhSa1E7sWZvs3p1X_QkMwg6rq45Y3A"}], "types": ["point_of_interest", "establishment"], "reference": "CmRRAAAA978ZdVX4gknvo6igjXxiLsDbCZtF3j_2yoaricg8f0pWBpoDEvu1UbIvUPRJq025FPZCLeXoRB3X4E1TN-oPSLplX69OYCDQrcaxhrAF3o-KdislA4FPt8tyrnPtvyGQEhC4uarwpPI2rn5mGNOIz8tmGhRB_ztEjiEPX8NS6KeK8OBGoGfExg", "name": "Student Conservation Association", "rating": "NA", "id": "1c5ea7722fc0d99e9f7dfca55f5d9078224d51d3", "job_title": "Phillips-66", "place_id": "ChIJQcqBXfDAQIYRErawO-goGj4", "address": "2990 Richmond Ave Suite #400, Houston, TX 77098, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-96.038102, 30.055621], "type": "Point"}, "properties": {"photos": [{"width": 984, "height": 985, "html_attributions": ["<a href=\"https://maps.google.com/maps/contrib/110279808588468038448/photos\">Peckerwood Garden Conservation Foundation</a>"], "photo_reference": "CoQBdwAAAOw7RSJUNKZ0KW7cffuTlLKDNX82JcQ2SrL-9sUCSzUJgD083Vu8Fsbqx5XeNiGlnpTivWVuVjVfX4C23y32a0PYja0OkAfknOgOqqCnNi6OOUhzo2aQuoaiz0M2kOhhmXy_qiTmKyLLSrcTlzTC-YPgG2MKAiaKdTtRaB1y6pEXEhCFrtqtvwxAfwPam0XmO2xBGhSd0jxOxEa8YBWEe4S9jzTAO0Yw1g"}], "types": ["park", "point_of_interest", "establishment"], "reference": "CmRRAAAA3dnwLHoxBsv_jVFY2VkZG_Y31UyN3g1STWTAaD-NNAwSWH8-ptZVGHrK_evhI5X4FCNrG1AJ1fESaqdEL5YrSGmTmyMUEYDfirTZPMTW-g1BVmEiNVP3_C3iAvP3lycpEhDgUOxk71SJo4IOTAXfgo1oGhRJBqoyILtWv2fVWpTU1VGFh2xxxw", "name": "Peckerwood Garden Conservation Foundation", "rating": "NA", "id": "e618a4c618cd67ce4f5fdc165f640220ab3b53b2", "job_title": "Phillips-66", "place_id": "ChIJmUR7pvHKRoYRIIl0o73bPGE", "address": "20559 Fm 359 Rd, Pine Island, TX 77445, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.64386449999999, 29.7515036], "type": "Point"}, "properties": {"photos": [], "types": ["point_of_interest", "establishment"], "reference": "CmRRAAAANG2fi2RZIQeUcthTWp-5B5oG6FOF_CiMI8DiivwVUrCVoiDOehDmswIDwYPd6-p0Is5JmFsMr588bnIObcUiQDIiRF0v0JUhJOysD0e20Qh78T-pFiEI9DdV3QWMLcAEEhD-ga1GR-SA1iXMuyip9FoSGhQtC3RLFvTCL5c-YVN3-9sBU0a1Uw", "name": "H2O Conservation Technology", "rating": "NA", "id": "30c07988ef8dfc62dac712b9d587daa4a36f2539", "job_title": "Phillips-66", "place_id": "ChIJIWZRKeHKQIYRXxta3wOMGGc", "address": "1725 Hwy 6, Houston, TX 77077, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.5705632, 29.7714443], "type": "Point"}, "properties": {"photos": [{"width": 3024, "height": 4032, "html_attributions": ["<a href=\"https://maps.google.com/maps/contrib/108143329814504597326/photos\">State from Jake farm</a>"], "photo_reference": "CoQBdwAAAC5jk48c4WSWBT_CMeSqKlpZqy87gpHH8CqZXixQDTqmCPXle7ksm7WYpkVAhSm1osuyaaL9y65Hs4aJF-we4Tpvlm6KafWfInpKwb4FXPllOeXtxvl80yfpDWrbx_ONxA1ysviADfUm1lOHihbnkWsysbylDEQOMh4PvqpPdKAXEhDCJPxxo6Di34j474FfUEEMGhQGjjDQz9gMAH8h99OyKIQGa9ZMCQ"}], "types": ["park", "point_of_interest", "establishment"], "reference": "CmRSAAAAVOiczHqam3-0yFdcknYhEPaH6TVsEJAIgpJ5S2W8F8-m4Kxq_iQ4xmfi5XFxFH1Q3jgDdGTgKuhSIx50P4VrrAlS7Z5gK4P1mKi0eMNPcRuzwO9z8hY53bffWKPvqB5dEhB1ZHdTLJ_fQoELpExYQg7eGhS5MJYGv0jZOGzNJHpe9jrwwiRnBg", "name": "Houston Audubon Society", "rating": 5, "id": "050a5458d86bdd1cee7b09678bd6256d0a20a73e", "job_title": "Phillips-66", "place_id": "ChIJlQOxwVDbQIYR2uX_TZl0TYc", "address": "440 Wilchester Blvd, Houston, TX 77079, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.56820189999999, 29.770778], "type": "Point"}, "properties": {"photos": [{"width": 1800, "height": 1200, "html_attributions": ["<a href=\"https://maps.google.com/maps/contrib/108765250995932379967/photos\">Audubon Docent Guild</a>"], "photo_reference": "CoQBdwAAAJwsEKIlvlQfhPdcgAhbSnjMKlH8okI9Gvx88pVv4UGX9GZbSb89AclTNi4R4dt_RP-gTW8drJGkzmdLHvVY_Gd8ekZnJqNNZD8GQma-zn1zGGx3PGZ2gAqu0Hlac1NLwUK_o9XnYDE13hJnctapR2zApx50fJAzVDe2bmn-iT18EhAmrDoa3PNMwsvi9dGhWrayGhSmJc9nbEYe6hcG9JsZVK_Sb11O-A"}], "types": ["park", "point_of_interest", "establishment"], "reference": "CmRSAAAAUCmvLs11a6Hf75LXYF-a_WS0DLTpesUKPutL8VkHS4BaeLSAkk6TUDM_Oi35oDXN0pPhL-O9O_363UENbEvWCsRzJSJn99HTdxY6eYqt0c8G0fsXnhqIejVxEpJ6JXuSEhBx0O0fh-SezyLRYNjG68xZGhS8E2IBjcy1oYzgKa4U_o3t_DFChw", "name": "Audubon Docent Guild", "rating": 5, "id": "7ddd5daf76cc4979e2ba6b062322d1c77d5d1c07", "job_title": "Phillips-66", "place_id": "ChIJI9XyNFHbQIYRtwHb8EtTpeU", "address": "440 Wilchester Blvd, Houston, TX 77079, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.44932349999999, 29.7803218], "type": "Point"}, "properties": {"photos": [], "types": ["point_of_interest", "establishment"], "reference": "CmRSAAAAL50uGUOm0ad1k7Lyob0RVkc9kaVDdC6cKeETiVRglkbaK3z9udoto7o0X0WD4nWEofzDUGXu_J7XdpHWf4Dc7WQF3G5I4NbKojayZM4GKmS4d6SuEIxBthiaLqmOBL4kEhCLdpPThVNwCz5y-sFOqIh1GhTvxetP7JNFfbgaof8x853AX0QF2A", "name": "Coastal Conservation Association-Tx", "rating": 3, "id": "7258b034e119f31e82320bca6e72781ee9f79d75", "job_title": "Brookhollow-Heights-Transitional-Care-Center", "place_id": "ChIJcekacM_GQIYRPzL13cgQrPk", "address": "6919 Portwest Dr #100, Houston, TX 77024, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.47039, 29.655454], "type": "Point"}, "properties": {"photos": [{"width": 5312, "height": 2988, "html_attributions": ["<a href=\"https://maps.google.com/maps/contrib/101184977609161362375/photos\">aug4</a>"], "photo_reference": "CoQBdwAAAF_V5s_kIlBtmty0njSEZIKPY_jIlvIQ9KaK8GKDroqtTlG9Kv_U0JPSOY_anM_MHH_X5YN7KkpB34HKZHjqN4AD24AlAAmiIhym4FAcixBulqsyY0WVqt_9HP8ZnITzvZRcg9Bev6sVegddpIBhJaYMrEhYkIghwp0-ZYw_q9XdEhCf_0tOys8pcxILpCIS21B5GhSOKijv-4NVVEASNLYolVCZtFlE7Q"}], "types": ["park", "point_of_interest", "establishment"], "reference": "CmRRAAAAlb-4zNk6bgYQLfWgQqEiaARKmSkETpuCoQLeLfWM5-L6CUZjUN55R6v7x2ljXj27exdrNB7uCh90kzg3NeV8hPHeSLlaDeGbCBvGWYl7UHDxoWBh19QUtnKi-twssMtrEhDTpqTB8F99GQeMfJ14NLhOGhS26iwO_tIs9u3l6MZX-lG3NsgTAA", "name": "Willow Waterhole Greenspace", "rating": 4.3, "id": "0127506e8071350c2d48f0ca56e939045297a0f4", "job_title": "Brookhollow-Heights-Transitional-Care-Center", "place_id": "ChIJR6_2zTzqQIYRsA7wExgfDWs", "address": "S Willow Dr, Houston, TX 77035, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.4003322, 29.7388505], "type": "Point"}, "properties": {"photos": [{"width": 1136, "height": 640, "html_attributions": ["<a href=\"https://maps.google.com/maps/contrib/117056878997299689379/photos\">Marisol Brown</a>"], "photo_reference": "CoQBdwAAAPjouLCWIz56uWHYkcUAq1sf8tyLYXvKMp8xvB58Rf4ESVYEfVdp2ipMuv4RXExSeoz5DjJUzXZ8wYifH-ngvxFutqCPeN7HDKH3WbRbYwXu95YHSpmnMOHszueoBG0vDO4MjvfA3K8ZdWqWoGGZeK54RhzwvsoyXxmcVKx1BZFDEhDuBl3POWMaHd75WBePfp26GhQxQc2r2089MTXtwpsTg4-Y6Y8iYA"}], "types": ["point_of_interest", "establishment"], "reference": "CmRRAAAAKPv2rS6tgz8n2GZkQF7RuxcrEjYtneNKbdqJNfFfcXS8viI79-E_nL9k6P6VqMLP7cWT0rtxi7zZnK9-yAClT5g8LNA04h8cPncO5Ltm4HPAFOZ_lti2jUUyKhSyyNC7EhAJsXrS9_YKCsiRMeUtYF6pGhSpXIAWDxqEo_qkibESYYvRB-C2jQ", "name": "Masters Fine Art Conservation", "rating": 5, "id": "a462c2eef4e22ea319485ae7b84f3d20756cbdd1", "job_title": "Brookhollow-Heights-Transitional-Care-Center", "place_id": "ChIJp8u2bZvAQIYRbosnWz6cVmY", "address": "1612 W Alabama St, Houston, TX 77006, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.3876169, 29.794149], "type": "Point"}, "properties": {"photos": [], "types": ["art_gallery", "point_of_interest", "establishment"], "reference": "CmRRAAAACRLbobtnYifWJsnpf50C3WPOTUm7PkvkZTleRxqUdfD-R3mjfgYyITs0HCTGw026pMZF8Bw2ouVPe8QxBXxejdZCmQabJ8pGKl8naIBqqAfL0xNaHH2P5SbLRMuMnpFgEhDdT3zszT8rIFmehVcgNgc7GhT097_TfFZ2AmT5HC7PHv6lPY3htA", "name": "Whitten & Proctor Fine Art Conservation", "rating": "NA", "id": "883a8c5ef35ab28e1630235ad65a6b16506a67fa", "job_title": "Brookhollow-Heights-Transitional-Care-Center", "place_id": "ChIJ8YuXE6K4QIYRn1SF1hazFEw", "address": "1236 Studewood St, Houston, TX 77008, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.3858767, 29.7300997], "type": "Point"}, "properties": {"photos": [], "types": ["point_of_interest", "establishment"], "reference": "CmRSAAAAxiFnRSiSne5vx0fldIHNJDJKzFIQcBM3X1r_mhvCZXD4LJcQwMW8pUzigeleGZ6D_2_w3CYoz08RZuIsSxo4u5DFpyx2Sg48CohY8Z6Zw90RpGXoRSSg7zyd1obt0Ep0EhDX35cGKXKo0NMVkDayIMvfGhRSupHdJsdroXUexGDzrog2Vn6cfw", "name": "St Mark Fine Arts Conservation", "rating": 5, "id": "ea2d4bac6d74716b33f456dff3aae0cc0b43cca3", "job_title": "Brookhollow-Heights-Transitional-Care-Center", "place_id": "ChIJKbDEoXm_QIYRcRFBlp0dE8A", "address": "4901 Main St, Houston, TX 77002, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.483218, 29.7482286], "type": "Point"}, "properties": {"photos": [], "types": ["point_of_interest", "establishment"], "reference": "CmRRAAAAgDzFrXDO-mWiT-lfdIoFxXCXoDm0nPEJOc5QBjWvmqBlzoXC-BXMA_gLHLdSnl3pXpeKXKxnnAiJXpg4ixmMp3ygWDeIch0_jtHyeUUAf4cG0Mt9MWJlVMMvqjmCuGUPEhDR0bC_2LazHkCGCEkju2_uGhQRiBnXNPTDPVkhUHklvnoEL1KBvA", "name": "The Nature Conservancy", "rating": "NA", "id": "90af6fb9fb926dde9f7103577cebc4150bbb1dec", "job_title": "Brookhollow-Heights-Transitional-Care-Center", "place_id": "ChIJq-m4EX3AQIYRJkn4Lhccp2E", "address": "1800 Augusta Dr #240, Houston, TX 77057, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.42318089999999, 29.7345943], "type": "Point"}, "properties": {"photos": [{"width": 750, "height": 437, "html_attributions": ["<a href=\"https://maps.google.com/maps/contrib/106788706324997826205/photos\">Erika</a>"], "photo_reference": "CoQBdwAAAH4eclVo1bHFyhZ9Af6Q4wBQ6-WeRri1y8ks24gRXjhdSfP0Pg3MAAMW7gfLAAyQtZqP3WJ9XOmxyKBHXvu99Hvcv5HSTSv7EwYVE-dz5XSEJU4bFR_1OUn3O7VliPhTbGw7Hb031EWo4nz9OEX_D1EJLaC9jmUDxWxdlJYzOYO7EhDknTqDvb9ihJxrASU6Qz9YGhSR-n2zPIpXM3MjHnA9sPaskPmkmQ"}], "types": ["point_of_interest", "establishment"], "reference": "CmRRAAAADYqm9JHSJ0se4MeuWCFA5TSdamd0i3WAs97W1LZIKxvutgFUuQVJmtPOpUt7uIMC7kWbzC4gW3ffvbQbBZeUbzYsiv82nZrfLSFvR-dpNdWdsfUTqnkL4gMcQed7-cZEEhA7clgDGCBedkwH1hjsybD-GhTffs6EkyFqP-K586w0lorHXUq6Fg", "name": "Student Conservation Association", "rating": "NA", "id": "1c5ea7722fc0d99e9f7dfca55f5d9078224d51d3", "job_title": "Brookhollow-Heights-Transitional-Care-Center", "place_id": "ChIJQcqBXfDAQIYRErawO-goGj4", "address": "2990 Richmond Ave Suite #400, Houston, TX 77098, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-96.038102, 30.055621], "type": "Point"}, "properties": {"photos": [{"width": 984, "height": 985, "html_attributions": ["<a href=\"https://maps.google.com/maps/contrib/110279808588468038448/photos\">Peckerwood Garden Conservation Foundation</a>"], "photo_reference": "CoQBdwAAANQOefM5ZF3CCEoBpB1Hz6WUVUMftlAzcebqWHOSs7msKH68uPddxzxnEK0OUYQUPQpe3mBbSm1s7sADsv39ygdywC-6qkiLGNjRfz0x1ETbrBr9XSChB3gX6l56dgpPec1cfNW-6sMCNQjUY5YAA3acMGH2l85_JfbrWUU4htWqEhD50jP0UFqHSQCgCuPt2UUxGhTFx36mEH7h2FujQVuw7Z08etyqgA"}], "types": ["park", "point_of_interest", "establishment"], "reference": "CmRRAAAA5etom4BmhqYlSuAJJPuRbVpkvchAsVVTnOdfi6l13gsWOLJPIw6c-cLsoc5QGqMQLvQVqkL7NcxM-NCU3agnSlz6plxFTOAAeBDuuRHx8lJiyCUpYC6tkOAH3DlZNHWeEhD_BNHm7_MzR3SE0nwEpx9UGhSFoHsx5gu0TP6rC80ubHWSSi6YwQ", "name": "Peckerwood Garden Conservation Foundation", "rating": "NA", "id": "e618a4c618cd67ce4f5fdc165f640220ab3b53b2", "job_title": "Brookhollow-Heights-Transitional-Care-Center", "place_id": "ChIJmUR7pvHKRoYRIIl0o73bPGE", "address": "20559 Fm 359 Rd, Pine Island, TX 77445, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.64386449999999, 29.7515036], "type": "Point"}, "properties": {"photos": [], "types": ["point_of_interest", "establishment"], "reference": "CmRRAAAA54pgos1beds21Ff1F4AC_c1nnuvjhVgKOyyZX8fx4tQz2NJasLB68Lag7Vmvnf_64mmG1Ao0P_h2fucl8LYiHdZwKVvIye-07NjwsdvKGwDlZZpyGWxAC10scmyhnaPpEhAoxHGm6n0EDdPCbimhzekyGhRwkQ1nDKPzuYByLF-RPW8FnS-crg", "name": "H2O Conservation Technology", "rating": "NA", "id": "30c07988ef8dfc62dac712b9d587daa4a36f2539", "job_title": "Brookhollow-Heights-Transitional-Care-Center", "place_id": "ChIJIWZRKeHKQIYRXxta3wOMGGc", "address": "1725 Hwy 6, Houston, TX 77077, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.5705632, 29.7714443], "type": "Point"}, "properties": {"photos": [{"width": 3024, "height": 4032, "html_attributions": ["<a href=\"https://maps.google.com/maps/contrib/108143329814504597326/photos\">State from Jake farm</a>"], "photo_reference": "CoQBdwAAAMpFznuFH8bqTBmJVh4S6mlCQg4y5m1UoGVLWMt_bGsOtnlPnQDLOWad0j6-gsiMREdjjT06U0wZh8G3QVn9fQWm56r_pqAaXd81ScKhUe5ffCd7jiidSHanMOFpktSixA5VGah4tZV4d71rrR5-cVRLjOPWc1VN1DGDGtdtQe0jEhDPy3teDc2nUuF2RhEEY4anGhSDioD63xUuevOCzwNnXp8qQAyrPg"}], "types": ["park", "point_of_interest", "establishment"], "reference": "CmRSAAAAoG5OYuzXvP6KQfZ7TP9VCC_Ftny7o8t_xoaWZ677SpWlehJdGjqKK3Npr6vaxBWm6Dmb0uwj7zIOWLbAKh8fGK-kzDQZgB3nRSb2ASrZCNEeRZ2PsFxuJvIRxhSz79Q7EhC-MJKzkW3uhMFzv7Dnr94-GhTEdVn5tJ0qfPlTjcpEnf4nb5tvhQ", "name": "Houston Audubon Society", "rating": 5, "id": "050a5458d86bdd1cee7b09678bd6256d0a20a73e", "job_title": "Brookhollow-Heights-Transitional-Care-Center", "place_id": "ChIJlQOxwVDbQIYR2uX_TZl0TYc", "address": "440 Wilchester Blvd, Houston, TX 77079, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.56820189999999, 29.770778], "type": "Point"}, "properties": {"photos": [{"width": 1800, "height": 1200, "html_attributions": ["<a href=\"https://maps.google.com/maps/contrib/108765250995932379967/photos\">Audubon Docent Guild</a>"], "photo_reference": "CoQBdwAAADB49UVI6vOCOSxrk9QueWnpadQ-AI-LRRiJQ4TYuHk6FnGWZ4ym_nOUC9vdEiDjV7naqaYY2X5WlxMt984A7CUmQQhuk90mENp9WWfyXJywzO-SOgUBqlHXgF-TbEFcodFPGC1c3x3gQt7qYAQEc_AyYsCPf_rGnWfc_GzjjNJsEhAYdaAzsy3FOn88huaQA_CZGhSkr3Dc4keU8EaUw2m3rvNPt2CmDg"}], "types": ["park", "point_of_interest", "establishment"], "reference": "CmRSAAAACvi_GOQi6NkTmHHVLpijgPQH5DplcwFviutsy-61ZtzKxO3CtKo8hpuu_cJG-a5jYoPQJgEdW8b1FTzY5ZYz3PIVgswWYqV3zk3XoG3lfhzKZA-EdikRbMEB7b79jEPVEhCZxLMIPUITBrBxFrLnubzJGhS6IL7M6vkeoYkdcrtTVWbHNn-wuw", "name": "Audubon Docent Guild", "rating": 5, "id": "7ddd5daf76cc4979e2ba6b062322d1c77d5d1c07", "job_title": "Brookhollow-Heights-Transitional-Care-Center", "place_id": "ChIJI9XyNFHbQIYRtwHb8EtTpeU", "address": "440 Wilchester Blvd, Houston, TX 77079, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.44932349999999, 29.7803218], "type": "Point"}, "properties": {"photos": [], "types": ["point_of_interest", "establishment"], "reference": "CmRSAAAAk_YBVHvVAyLmx0_VDRy8-ZMTEWOrQ9rnHdUoRZT0m9Le5aQYVZGkzJvkhq_R6h1APu1Mhh1PljS_wjKUHOCL5NLehi_5BSONPTyQAyc3sKnbodeVSetIdSShCaNSuPJeEhBWOc3WUn-1n5tX8Ne5e735GhS_JjuhA0IgGGw2WzynbsoBFs0cYA", "name": "Coastal Conservation Association-Tx", "rating": 3, "id": "7258b034e119f31e82320bca6e72781ee9f79d75", "job_title": "Erm", "place_id": "ChIJcekacM_GQIYRPzL13cgQrPk", "address": "6919 Portwest Dr #100, Houston, TX 77024, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.47039, 29.655454], "type": "Point"}, "properties": {"photos": [{"width": 5312, "height": 2988, "html_attributions": ["<a href=\"https://maps.google.com/maps/contrib/101184977609161362375/photos\">aug4</a>"], "photo_reference": "CoQBdwAAAAebTW20rJaEN-HYsOPRhA9s_MivgD4v3jlo0mKf4RWD2j33x1Y_P-jNgODqnP2L6vMa57Uk9EL2fgQ2Yw99PUYtIIl_WDgTGNDy-pU8fv649jbiiEcglstZGyrPDiP9JWhE9S5IDJBV1JAkbtCl-86A8YX-oxtbd2kSPwirJ5K1EhDqQirlsbakJuWBkkBnMIupGhSHQZVfKCUShmd2r1aylqLmYNMHYQ"}], "types": ["park", "point_of_interest", "establishment"], "reference": "CmRRAAAAfni15D67iiMwo97a50x0Nr7o_6QKytWoElMABjChr3r8ktFu5I-GfQ-UnLE4ZfbqolkXodg55d0Xv2QKmF-QUpfZMxP0rLWVsGHgYMU1_XT8lmFWpYpRb4heAPxxETgWEhAGmfbii7D9ogXg7iIwjgz6GhQboAPlvLeh0XYV4tmbWNNysvbDpA", "name": "Willow Waterhole Greenspace", "rating": 4.3, "id": "0127506e8071350c2d48f0ca56e939045297a0f4", "job_title": "Erm", "place_id": "ChIJR6_2zTzqQIYRsA7wExgfDWs", "address": "S Willow Dr, Houston, TX 77035, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.4003322, 29.7388505], "type": "Point"}, "properties": {"photos": [{"width": 1136, "height": 640, "html_attributions": ["<a href=\"https://maps.google.com/maps/contrib/117056878997299689379/photos\">Marisol Brown</a>"], "photo_reference": "CoQBdwAAACKv4vGO0k0QN9sILaREp1GVNis-1oNoawa88EC0dKHdgELkHgAmR54Z9zrF9QhO_2LZoNKh9gJ6u-DEiuYSAaWQ3ntgLtLWsqZwH6CXEOCY-HoSIvCszKUXNFpeGX7Gt8I80WABhAcowpO0v7Q4AtIasLWcIb-bjpkrGG64cgr3EhA1G4UxOfcqC8gDTJBr9-igGhTMs4bvbopeJlItVUWx20e2KShT8Q"}], "types": ["point_of_interest", "establishment"], "reference": "CmRRAAAAen6zMpamFURxtZPttyxrUeMbr3pv2Tn8Z7-B9kfXIFX6wKy9eAtFzbu1JmVtsfUNZMh4xzX39aEmgN4srf3_qWXZuxScURqlQU00FJXtbRj9DeWX9IQ5aa8LovEJCrfvEhBbipPJFUA-lwmmdJCmZSIIGhRPveAhwGV8CUK0p3Ca9c9yPJrkoQ", "name": "Masters Fine Art Conservation", "rating": 5, "id": "a462c2eef4e22ea319485ae7b84f3d20756cbdd1", "job_title": "Erm", "place_id": "ChIJp8u2bZvAQIYRbosnWz6cVmY", "address": "1612 W Alabama St, Houston, TX 77006, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.3876169, 29.794149], "type": "Point"}, "properties": {"photos": [], "types": ["art_gallery", "point_of_interest", "establishment"], "reference": "CmRRAAAAtAwBKhs5fBF19HJmrVH5MGahDp0-9ZCcDd9z9lXlIfrBwTT4d_gsv8gLS9x1Wbt2LLXXF1yu-3Bt8VBPkOPIh5SneWh9i6myR9zfKIxiW3ll_wLNAiCincrnZ5Jbtz_0EhDJexJFfKGmm9H-GkV7OElmGhSu6HLLXRTxWFZRVKYIVk0XYGeqUw", "name": "Whitten & Proctor Fine Art Conservation", "rating": "NA", "id": "883a8c5ef35ab28e1630235ad65a6b16506a67fa", "job_title": "Erm", "place_id": "ChIJ8YuXE6K4QIYRn1SF1hazFEw", "address": "1236 Studewood St, Houston, TX 77008, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.3858767, 29.7300997], "type": "Point"}, "properties": {"photos": [], "types": ["point_of_interest", "establishment"], "reference": "CmRSAAAAL5Wx6TpOIeKrklEkC5lWu1ZfdRMRMA5M6OGl_Bvpx7xIksGXcjL9ZFYDBiMsaOHgf_uBub-Kg9nNSthyo6ngC6reVm2aEZcwDjHPevFXd_hnOO9Vh_8vuvQBqG3Qi5ZZEhDaEoq3UQHl2I1xLuEhbvToGhRVL2uVvHIWznQPfkvLeug4jOnXYw", "name": "St Mark Fine Arts Conservation", "rating": 5, "id": "ea2d4bac6d74716b33f456dff3aae0cc0b43cca3", "job_title": "Erm", "place_id": "ChIJKbDEoXm_QIYRcRFBlp0dE8A", "address": "4901 Main St, Houston, TX 77002, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.483218, 29.7482286], "type": "Point"}, "properties": {"photos": [], "types": ["point_of_interest", "establishment"], "reference": "CmRRAAAA9Mb01RXZuzL6_EUWeJYc-HF01u5oJQ4akfgUcmSkf7Y7F9gM1ybC3aO_IHdXZYLbBo3zJpIGD6yzDV6GHXFraDcl0rpU6VWHhvRzxIP8EtUbHt_SelsQw_mU03vHpJ5_EhAaOE1_XpK_oywb0g-bFV6SGhRp7AQyYgWEd1z9clKzLtEr_ckB7Q", "name": "The Nature Conservancy", "rating": "NA", "id": "90af6fb9fb926dde9f7103577cebc4150bbb1dec", "job_title": "Erm", "place_id": "ChIJq-m4EX3AQIYRJkn4Lhccp2E", "address": "1800 Augusta Dr #240, Houston, TX 77057, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.42318089999999, 29.7345943], "type": "Point"}, "properties": {"photos": [{"width": 750, "height": 437, "html_attributions": ["<a href=\"https://maps.google.com/maps/contrib/106788706324997826205/photos\">Erika</a>"], "photo_reference": "CoQBdwAAAJ4NzH2R2XuBuP5oYJ1wBSnOVT0kDQuh_gTyKXR4RPuQvaPBX86L7SqqFyHIZpBX9WIbd9ibMiJOjKy_xlVBDXWHf5P5_7bm7XVKnRSxQd0q7lJ1YyeG0YGVZ5-pgWsyE8c6825ixR2fL-FjsOdCpq7F5y2RDcdXuk8JDtAoelEBEhA6MIbxF66cAfiXkJlXISdGGhRllCd5tQUoIi6UNWogXQc5GNd4qA"}], "types": ["point_of_interest", "establishment"], "reference": "CmRRAAAACVDsCUXuP1ds7PuAwrqfyeU2CrOMYSra7uKu3YL7SC4vr6pHhLUZmAy9fJpeB_SkJyA1X2Nd_pXyFv_s93Ql3lzOTBGjFPWjAZucpIK_0o1PdACI427MdNCmk9Xh3GJVEhCbT5JTbiseDOMkhAHqGhCgGhT-Rf5LryToEyslabdFtnzzGzotpA", "name": "Student Conservation Association", "rating": "NA", "id": "1c5ea7722fc0d99e9f7dfca55f5d9078224d51d3", "job_title": "Erm", "place_id": "ChIJQcqBXfDAQIYRErawO-goGj4", "address": "2990 Richmond Ave Suite #400, Houston, TX 77098, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-96.038102, 30.055621], "type": "Point"}, "properties": {"photos": [{"width": 984, "height": 985, "html_attributions": ["<a href=\"https://maps.google.com/maps/contrib/110279808588468038448/photos\">Peckerwood Garden Conservation Foundation</a>"], "photo_reference": "CoQBdwAAANlEi7MRchhVAI3i3W9cwZunrfOao2-8jXsO66J0qK_PntpimsX3eApUXIzBAZcJWFLWxiHOxpEc9_d7Sv5OIaWhEaVdcYvPd5bUxIWSN7m19YClv4M4xzGwMNYTiLg2WK1Too_vMCoktdEvhxEFciO5dwFe457AUB0yo5iP_LMNEhB5xAKaZuoaw5Z9BqlVNCwVGhQZ6ftwgemZ5E3X7PDagaJlt7KL1g"}], "types": ["park", "point_of_interest", "establishment"], "reference": "CmRRAAAAHy88h3P0eOGAF6TJbDlXD1SnLlqFqyeLDZATRylXVJt-qlKWaEGGpzxb4MMoIvC0YcDQcBgIE7rfJ545Vnj5SfQyUkQRJwOTyBuo9qMrpe-GJcbxrVQYyPPxgpZDzaqGEhC7c5J1niBUkKBB1BuY6JfzGhS5UUYXJs0LmbPQg9lAaYACu6vV_Q", "name": "Peckerwood Garden Conservation Foundation", "rating": "NA", "id": "e618a4c618cd67ce4f5fdc165f640220ab3b53b2", "job_title": "Erm", "place_id": "ChIJmUR7pvHKRoYRIIl0o73bPGE", "address": "20559 Fm 359 Rd, Pine Island, TX 77445, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.64386449999999, 29.7515036], "type": "Point"}, "properties": {"photos": [], "types": ["point_of_interest", "establishment"], "reference": "CmRRAAAAuNZnfpvtf2PsJkK8N9-uM9rmJylj_BNezmKZuAAh8NU95GJ-E7bP9ZXghexMVTPsKJSwLe5SL4ag-byMW1OW9ex0TjQp3LoBziPCrApfqaRs5LGwrvF56gsa8D66E5RQEhD7C3onvYD6znJbULer3xRBGhQEbjJCOGpVDVCR0C_BUfscObr7DQ", "name": "H2O Conservation Technology", "rating": "NA", "id": "30c07988ef8dfc62dac712b9d587daa4a36f2539", "job_title": "Erm", "place_id": "ChIJIWZRKeHKQIYRXxta3wOMGGc", "address": "1725 Hwy 6, Houston, TX 77077, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.5705632, 29.7714443], "type": "Point"}, "properties": {"photos": [{"width": 3024, "height": 4032, "html_attributions": ["<a href=\"https://maps.google.com/maps/contrib/108143329814504597326/photos\">State from Jake farm</a>"], "photo_reference": "CoQBdwAAAFIC_yeeWVcfTyYsyZ2fuM4UXp70n_Ai3y2zgc3iyOXJ3r9LldupG0CkXvu7Kai7pXAgO09zdkurnfwakHjAK9V2wRIq99Z_0dln5d2sD1tIVqB8Yg8yd_iltue_ov9XBF4Nthpekc0Mfaq44K5db4PR0479h9rmYoDQPkfFxvXwEhBoWaic7aG3cSvatXVzgGhaGhTiRK6GhY1Tvig0tAVuerlFrgCjjg"}], "types": ["park", "point_of_interest", "establishment"], "reference": "CmRSAAAAg4CLSqP6SLj8b4lGUrDsPFZMIznIrda9x2K7DcePjYFxpv-N37mghslUsfxpENKszLnOMglsJSh7r1sWCjqPFidleDMlDkzTJEpWJLsW5_ZMwNDMvZPUBlRoUAppXiO4EhAoTtrgB3jyP6zhs8YSg42TGhS6MIqe1DbSpZVu01slYpt8XEtkrQ", "name": "Houston Audubon Society", "rating": 5, "id": "050a5458d86bdd1cee7b09678bd6256d0a20a73e", "job_title": "Erm", "place_id": "ChIJlQOxwVDbQIYR2uX_TZl0TYc", "address": "440 Wilchester Blvd, Houston, TX 77079, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.56820189999999, 29.770778], "type": "Point"}, "properties": {"photos": [{"width": 1800, "height": 1200, "html_attributions": ["<a href=\"https://maps.google.com/maps/contrib/108765250995932379967/photos\">Audubon Docent Guild</a>"], "photo_reference": "CoQBdwAAALEJzGx6fnpHXvih0A1WQbxg57w-T-kzm0mK0UdcFwcjFextlMIxnCLMRy_BzcSXPFiitg513F-H84G7tsZJg9L93ZjImC2jyLKcQBXS5htBVP00tuOLV4fA0hneST7roYh4rWSDM-FoAJbGWJstQnVk0w5K8_dMDLBH7SSIobzAEhDolHtshSiLVlBUbMs836rsGhTL8BBBMayO8JAdWEa5hagz-3BdHw"}], "types": ["park", "point_of_interest", "establishment"], "reference": "CmRSAAAALhs3B2uksNTunq5ho5v_dXBQNYptaz7NzCDgGuMg3BTayZk0Nl3hHLU2XiAIa3nsFybx34udb_q7ju0zB0Pcy8haSUdVnrSg7SvXokikwleQcqUEnZXhPuu7YBAsjg46EhAx_sfnVW9v7_9CAS6dOpsnGhT7UkLMQRjz_vvyF4psFk_uryKTRQ", "name": "Audubon Docent Guild", "rating": 5, "id": "7ddd5daf76cc4979e2ba6b062322d1c77d5d1c07", "job_title": "Erm", "place_id": "ChIJI9XyNFHbQIYRtwHb8EtTpeU", "address": "440 Wilchester Blvd, Houston, TX 77079, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.44932349999999, 29.7803218], "type": "Point"}, "properties": {"photos": [], "types": ["point_of_interest", "establishment"], "reference": "CmRSAAAAtOoyejUcsHVqpVx4JzpReOUPqads-_-C6Z2BcBYySH6Krm5PHdV_Pue_rIyq5G9Kgt8i0vQfy7G0kSQZsfOAjh5umab9U087E_RsVWiloXWLehWIq_155kQrHTEWYFCUEhCV-xHWRSGFQeBNkuuG-9IdGhTk5v-hovnwCzLCteVZu33b407d-Q", "name": "Coastal Conservation Association-Tx", "rating": 3, "id": "7258b034e119f31e82320bca6e72781ee9f79d75", "job_title": "Arch-Aerial-LLC", "place_id": "ChIJcekacM_GQIYRPzL13cgQrPk", "address": "6919 Portwest Dr #100, Houston, TX 77024, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.47039, 29.655454], "type": "Point"}, "properties": {"photos": [{"width": 5312, "height": 2988, "html_attributions": ["<a href=\"https://maps.google.com/maps/contrib/101184977609161362375/photos\">aug4</a>"], "photo_reference": "CoQBdwAAAEQ41JlxthboCfA9gQHktz2YuXQYH47a2BcGKwoX0dhlzos3QvnZUq6vQhteqsOw6QE7VJW3phXIjdWzHJ2u5LCNaSWTkvDrkJZmKAFs4omO-Ei18gEeVU1t4D6f1cwVWmqpeVCseDJP11ogyAqkiM9W0yS7VPNXCKUHAwiPU_1oEhDBuYgdGFrlvGdny9BrKdciGhRP3UHgKjb79DziKOm29hEp9KNVXA"}], "types": ["park", "point_of_interest", "establishment"], "reference": "CmRRAAAAPTQz6ECf_OYq9TpEz4AEWYgzf8AKB2pIGXZWMNiLCGpl0EKaHyTKoBbXxdafKjvw_u-DFCqkuwi9zxYZUCA2drADfWrhEigj_w6WcVC5rgKeMbonLokn-0Cbsf1lgk7CEhARXzvNeAprQL6w9juCM05mGhQR0TKcEV4TJ7maPFILanVUeKlpqA", "name": "Willow Waterhole Greenspace", "rating": 4.3, "id": "0127506e8071350c2d48f0ca56e939045297a0f4", "job_title": "Arch-Aerial-LLC", "place_id": "ChIJR6_2zTzqQIYRsA7wExgfDWs", "address": "S Willow Dr, Houston, TX 77035, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.4003322, 29.7388505], "type": "Point"}, "properties": {"photos": [{"width": 1136, "height": 640, "html_attributions": ["<a href=\"https://maps.google.com/maps/contrib/117056878997299689379/photos\">Marisol Brown</a>"], "photo_reference": "CoQBdwAAABGB6q4Mqc71TchAO7WQT53HhyvAkD2kPbglp5z-Cc_piJlicGpIh8SYKSexB4dvBD1-MPmZYQJiaZclWZyOzmfhWCX_nNsR0-EOtk3pbqjTmZfB4DfPRpYScO_cmyBWWqs5ZhE9umOL74IIIDkDA4v_Hr4KzaWfiB8J3jTHlICTEhAAZ7rYyiUF_Yk6mjXkJssGGhT--aIbH3wP39AgPq55bWkzODu-ow"}], "types": ["point_of_interest", "establishment"], "reference": "CmRRAAAAP8L1oTNBEXpTtn-b_FP9fAwp4rFILA0vaVzDT-yDqLQcbx-KlVhcfC8hRgSTPYfrO8jAeilbhfYpUgvRhNkfCoPCWjRNB4SlImDyK0WAaRliqCb3VsCVewbHDdAz20SaEhDwLnPJSxrBEBDVic3JjshhGhS1qIkAJesQUo67Cn7di23J39bxPw", "name": "Masters Fine Art Conservation", "rating": 5, "id": "a462c2eef4e22ea319485ae7b84f3d20756cbdd1", "job_title": "Arch-Aerial-LLC", "place_id": "ChIJp8u2bZvAQIYRbosnWz6cVmY", "address": "1612 W Alabama St, Houston, TX 77006, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.3876169, 29.794149], "type": "Point"}, "properties": {"photos": [], "types": ["art_gallery", "point_of_interest", "establishment"], "reference": "CmRRAAAAwVDp0frgxYXwAksjBvH8enLKpjYeMowYwvydyHALsIhZmUENQMtK1m-AJFZ9hy6KR6sGy44HAlDh4Uz1uJcAZgtf-64MBBcANnh7uPR93cD_C0MOFJXVOH5Nuf1sFMPtEhB-hmsUg8TG9fgDltXIrALIGhQM42-yf_P-fUqbwPUqnB1ALBkikA", "name": "Whitten & Proctor Fine Art Conservation", "rating": "NA", "id": "883a8c5ef35ab28e1630235ad65a6b16506a67fa", "job_title": "Arch-Aerial-LLC", "place_id": "ChIJ8YuXE6K4QIYRn1SF1hazFEw", "address": "1236 Studewood St, Houston, TX 77008, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.3858767, 29.7300997], "type": "Point"}, "properties": {"photos": [], "types": ["point_of_interest", "establishment"], "reference": "CmRSAAAA-8Q_Fym5GceWetNFCQciFeEBl67-qIw3MEF8pEAEwZJBAmISQAyHBzcpiYK0byyUwddtGlwmSfNXv0U-jGwBWDipPSRWBg3VKjeqkp9W4fq81YYnn4cxDUtB_-4eWPs5EhCC9iVdkVS-AHQt0GiewSYGGhQlrmFNEG0iXzVmLqW7vesSCgLQzA", "name": "St Mark Fine Arts Conservation", "rating": 5, "id": "ea2d4bac6d74716b33f456dff3aae0cc0b43cca3", "job_title": "Arch-Aerial-LLC", "place_id": "ChIJKbDEoXm_QIYRcRFBlp0dE8A", "address": "4901 Main St, Houston, TX 77002, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.483218, 29.7482286], "type": "Point"}, "properties": {"photos": [], "types": ["point_of_interest", "establishment"], "reference": "CmRRAAAAMG1bLmNICxWb27rA41Ya7GZNrsrXtGX-fuY3Bt9xvV1-OLYbEtzhUiXL9bOy9eFLFlziavFPyT5ZfUtTBcubt_1yaxwOgbtf_mcZcsyJ8bGKo8lfvxcm0Of8Ms3gP-WsEhCPZj38Y68QE68YHaJmCaDSGhQUvXqobeVV3tJVkFi68_sekMwMPQ", "name": "The Nature Conservancy", "rating": "NA", "id": "90af6fb9fb926dde9f7103577cebc4150bbb1dec", "job_title": "Arch-Aerial-LLC", "place_id": "ChIJq-m4EX3AQIYRJkn4Lhccp2E", "address": "1800 Augusta Dr #240, Houston, TX 77057, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.42318089999999, 29.7345943], "type": "Point"}, "properties": {"photos": [{"width": 750, "height": 437, "html_attributions": ["<a href=\"https://maps.google.com/maps/contrib/106788706324997826205/photos\">Erika</a>"], "photo_reference": "CoQBdwAAAFQ6zCMrrfhnCw7Ouxoh5xIaEf0U9ABBND4v_6eQEczPzQ1gCEvfIOlBedUxma0zAru_f2aIM8aVXLEVblqa2UNwGAvSL08LiaqQveUrxhDiHHH1FnoS5Nn9p__CIrN3xZCD1qPQwaf1KTsHV4af0fye1z5PduvvL_0e0RC4WNUMEhCm0FJov_G_5WVRYKlsk9W8GhQ1cf7cFVRL-DS1e8rOC63THcCZ6w"}], "types": ["point_of_interest", "establishment"], "reference": "CmRRAAAAxLEcEU79EQvcSZe5hTqOORCqwzUNerH4OjkxP4meGTxwDqMl9aQXHJoSdTu6dhNn3LI0Z0I_SA-sHfPf-3I9hYDRzlY6LlqQStKK6hajpmIruFa-CybPpDxcMn2QYEdwEhBpPO88Vq3EtoyKpzoGGAsvGhSM9YlPtwgZFas4L801gABGQMC0YQ", "name": "Student Conservation Association", "rating": "NA", "id": "1c5ea7722fc0d99e9f7dfca55f5d9078224d51d3", "job_title": "Arch-Aerial-LLC", "place_id": "ChIJQcqBXfDAQIYRErawO-goGj4", "address": "2990 Richmond Ave Suite #400, Houston, TX 77098, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-96.038102, 30.055621], "type": "Point"}, "properties": {"photos": [{"width": 984, "height": 985, "html_attributions": ["<a href=\"https://maps.google.com/maps/contrib/110279808588468038448/photos\">Peckerwood Garden Conservation Foundation</a>"], "photo_reference": "CoQBdwAAAPx32kUKif46pOGL92qpZ8sJAPzAm3lg-6SlqCDkXuxiDHbxB7hDVdVMuor2-Sba4YfERWUHDpkJcIPhMZIdAkeZpDRK4guwPflx3e6idGH8lC621KmOUV53HbreFrEkB8Ut_wVHt6D3FakrdMbB3lT-ghsxMw_lMq_g4IMoa85hEhAJpW8I0KPM7sc2jVTdJXqeGhRZLJebiEY5tItHiItYUg_IziApwg"}], "types": ["park", "point_of_interest", "establishment"], "reference": "CmRRAAAAGv5qlW5BEdqlNbagMAaKXdcMkXY4LxzUp-lgJRxdPgCTQQiLw1N2U5aBxiLEcv0Ex3H0RXRbKxA6CiLWjrF6gUwdIhgt-ETIbL2Zw93AGlo-0CXP8J74_KjjGJBgZQ9REhC5xxcUfDqxs3pewSCBvITGGhTC0pGnZD2caG9dtpdWurJnKVz4Yg", "name": "Peckerwood Garden Conservation Foundation", "rating": "NA", "id": "e618a4c618cd67ce4f5fdc165f640220ab3b53b2", "job_title": "Arch-Aerial-LLC", "place_id": "ChIJmUR7pvHKRoYRIIl0o73bPGE", "address": "20559 Fm 359 Rd, Pine Island, TX 77445, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.64386449999999, 29.7515036], "type": "Point"}, "properties": {"photos": [], "types": ["point_of_interest", "establishment"], "reference": "CmRRAAAAYrMXsXB9FK4ajhU2GO90ZwFbz31eZ_c4UOTKmpu0CS_L3T-f24l-UgK_1dkqcjxWQiR5wf0l2C0Vvg6FuLIyzRWtdfou45dVOXhKl5IbxFFL2pnxwwZufr1qAJTScM_zEhD7gQLPaCtsPnQEGK8yH_cgGhSnreFrJ2kmQLWDpO0oNvAUCa72Kg", "name": "H2O Conservation Technology", "rating": "NA", "id": "30c07988ef8dfc62dac712b9d587daa4a36f2539", "job_title": "Arch-Aerial-LLC", "place_id": "ChIJIWZRKeHKQIYRXxta3wOMGGc", "address": "1725 Hwy 6, Houston, TX 77077, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.5705632, 29.7714443], "type": "Point"}, "properties": {"photos": [{"width": 3024, "height": 4032, "html_attributions": ["<a href=\"https://maps.google.com/maps/contrib/108143329814504597326/photos\">State from Jake farm</a>"], "photo_reference": "CoQBdwAAAMtEaYEQoxs32RtTYiRl3cuDNp35L5UoeBedCw-bkIgt1L_gD66Y7WNnR0T-4OFq8ZI329Gp7OR1S3WJsxHHI6p_GYyRidRuR4VUqYN_Mdw_QuTY9Qasu0pISfo7tWxg8um4T_wpZe9d3ryYIiPUM3a7KrbgrFllf_aV5ISD-RipEhCXdJovqa6E2u8SVK7LQaINGhTsUvmIMsCUEmg-Bqi-2XvB5Wf1NA"}], "types": ["park", "point_of_interest", "establishment"], "reference": "CmRSAAAAo6ainiIaRBiR-2NCWloPhya3CWwumxQGymRbbtNbpi_biPrNUZmoIApDGgdjKpCLlv_01Q8pvi4GpbZdAyNgWMdBKC_6_4XIOKgsMEnlpzOatI7w5Q_Payf5NlaK8hIFEhBFWUynLbvTq6OI9uJhxWQUGhTddRlD7zlf20iZp-j18dodLONf6Q", "name": "Houston Audubon Society", "rating": 5, "id": "050a5458d86bdd1cee7b09678bd6256d0a20a73e", "job_title": "Arch-Aerial-LLC", "place_id": "ChIJlQOxwVDbQIYR2uX_TZl0TYc", "address": "440 Wilchester Blvd, Houston, TX 77079, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.56820189999999, 29.770778], "type": "Point"}, "properties": {"photos": [{"width": 1800, "height": 1200, "html_attributions": ["<a href=\"https://maps.google.com/maps/contrib/108765250995932379967/photos\">Audubon Docent Guild</a>"], "photo_reference": "CoQBdwAAAF5WWYAAW8_jyfpz_cFHuWNKzQhO3MTDuxI723vLJyGCeNneDKISUAv5foryMnYNQQrUc7fK-spd9t-ONUL3XvNcQzAI1bOoDDGeuRDLGll80PvC2isvuc3yeaa991XjZ0ETuW5VK_OJGnRSdG1hgc9e5S3bfnJN0GqIk7SFs_ukEhAVmEkkWUIE4fwSewkkQq2hGhQFOCDluhPJyamoGmBs3wBrxWqicQ"}], "types": ["park", "point_of_interest", "establishment"], "reference": "CmRSAAAAhCISVB29xZVkpomk3rmiBKhDMdtH8r9LU87T-jxwbaoioPRMiIx6TXiZqwXtRwWSuW-71TuJW9ZuZKYA9nMLvZBz4YHO_UNaSx6amkfi6MxZvIbKIzq27JJvkwFUXNoTEhCZwzv5v72AdDOUEzkgjIJ9GhRWm_dSJri1ZoYkaPAdi56luJFiBw", "name": "Audubon Docent Guild", "rating": 5, "id": "7ddd5daf76cc4979e2ba6b062322d1c77d5d1c07", "job_title": "Arch-Aerial-LLC", "place_id": "ChIJI9XyNFHbQIYRtwHb8EtTpeU", "address": "440 Wilchester Blvd, Houston, TX 77079, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.44932349999999, 29.7803218], "type": "Point"}, "properties": {"photos": [], "types": ["point_of_interest", "establishment"], "reference": "CmRSAAAAvgCf_qBN2PU728pYAvcIFDbg2qCplE-nzcqvLYKaGa0hpMEfoZVi0bdnphm2_ueHFxnmeWt9VUz0sPSwWKoi0x2aPaY5oNGhtwjVpEBrZFpkpudygcmtFmiPdMLhK95tEhDb-SANhxMSB7OiW_ZamKgzGhSzRahKd9v-pM1MfpyQ_UbovqZDlA", "name": "Coastal Conservation Association-Tx", "rating": 3, "id": "7258b034e119f31e82320bca6e72781ee9f79d75", "job_title": "Nextgen-Staffing", "place_id": "ChIJcekacM_GQIYRPzL13cgQrPk", "address": "6919 Portwest Dr #100, Houston, TX 77024, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.47039, 29.655454], "type": "Point"}, "properties": {"photos": [{"width": 5312, "height": 2988, "html_attributions": ["<a href=\"https://maps.google.com/maps/contrib/101184977609161362375/photos\">aug4</a>"], "photo_reference": "CoQBdwAAAGnIU7DbqvyTQ2NZkJXcZOGQhoC2vv2SHQ5E6C1unaDEkow9lPgjn2VSSjRIs4p59cxcMbMlodzv9FIbI0owtgiAGPHED0-DBmLiBFvQQ1orZe_qlaA_NJqA6DZhDY3bGBHuYusVBOXAx8aaMKAskf-MFt9kcwFQu2GfvemyRUwyEhAdYRyiD9jnHo5gPCg8Q20lGhR6bVBbuFbI4RBJzrhU-GPARRpt0A"}], "types": ["park", "point_of_interest", "establishment"], "reference": "CmRRAAAA7yoqvHF5Ht16AVQFWQHElmOdC9tOSEydiZHHAkZ-bB6nNEZH1OYSV99COGVOeZNVxzCt08jwK3w25qMEKruXpaQ2u4dLYRuvmY_h908Cum9rIxc5eBWvzasXvFRYsSWcEhDPzZ7yUwsYudsi1anV0Ia4GhThTkDzhLnd0pGsGoO--AOE9A9gqg", "name": "Willow Waterhole Greenspace", "rating": 4.3, "id": "0127506e8071350c2d48f0ca56e939045297a0f4", "job_title": "Nextgen-Staffing", "place_id": "ChIJR6_2zTzqQIYRsA7wExgfDWs", "address": "S Willow Dr, Houston, TX 77035, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.4003322, 29.7388505], "type": "Point"}, "properties": {"photos": [{"width": 1136, "height": 640, "html_attributions": ["<a href=\"https://maps.google.com/maps/contrib/117056878997299689379/photos\">Marisol Brown</a>"], "photo_reference": "CoQBdwAAAAQZoM5s7U5W2iR5gJJOa_nN63V95OqGYN_aP1b-1_sVwguFlfVdXFLk8eAGZudP02kVAO8yYtrOvCFkZhnNLS1CSygDN1pCYbHCo4K4Z2svhVH9N8qpQ5DVb07TIL9RvH7UKFebZR2OWnY-ryZ2wR8bJVrFcIBuT0RW3nfzewCTEhAdNym-NOzkdl9dQxT1eVWUGhQpPCYvXugs_dODApQN9oyFWQ4OZw"}], "types": ["point_of_interest", "establishment"], "reference": "CmRRAAAAIyMtW-M7iQEXYc9kOSdfE_VCvAbJUfxrKIzjUEbQDCV6mf3T7e1PTyNy9l2CEHDAD_rJL-1z0eI7J-WxMgJ8zzCTXq844csqe4O12ChN2a7QFmlaPbwghG7Pcdz9ZkjVEhA5vYGjKwwz5sgsIFipmwNaGhQvDSCDXow9DuXCp-1welycQUHKJQ", "name": "Masters Fine Art Conservation", "rating": 5, "id": "a462c2eef4e22ea319485ae7b84f3d20756cbdd1", "job_title": "Nextgen-Staffing", "place_id": "ChIJp8u2bZvAQIYRbosnWz6cVmY", "address": "1612 W Alabama St, Houston, TX 77006, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.3876169, 29.794149], "type": "Point"}, "properties": {"photos": [], "types": ["art_gallery", "point_of_interest", "establishment"], "reference": "CmRRAAAAooeFj-gPF-TDRlv5I0qGUVpHsd3KLPXUL9sRfNvPf7Y1INi84kiVT52CSjBfhtuvexwjr-LvZgQAcq2hKmEIxpclrlfH7LCTCl5tlqKkomO2XuiblQezsvoIODeks0XlEhCs8jBQjsx5LtUUiaaNcpBlGhRAGYF6rOy-I6V0BNNgHjdoqshtZw", "name": "Whitten & Proctor Fine Art Conservation", "rating": "NA", "id": "883a8c5ef35ab28e1630235ad65a6b16506a67fa", "job_title": "Nextgen-Staffing", "place_id": "ChIJ8YuXE6K4QIYRn1SF1hazFEw", "address": "1236 Studewood St, Houston, TX 77008, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.3858767, 29.7300997], "type": "Point"}, "properties": {"photos": [], "types": ["point_of_interest", "establishment"], "reference": "CmRSAAAA8kE-KikT8_9uuBJeWcYtgwzD5PT_G3YZvVmut8gvqnccZGdenuOdX6kWKqQQtVqhqhWQ6_7l3ZwoFCaGuRmfdwy9sdB2wvtaeuO-g0QNW0YduGRqiqi9MS2fNCzy210hEhDZntN5pGX4hWc2UYHqR-xoGhRUKfqIOtyjxFyt7GQRA4WJr7t3QQ", "name": "St Mark Fine Arts Conservation", "rating": 5, "id": "ea2d4bac6d74716b33f456dff3aae0cc0b43cca3", "job_title": "Nextgen-Staffing", "place_id": "ChIJKbDEoXm_QIYRcRFBlp0dE8A", "address": "4901 Main St, Houston, TX 77002, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.483218, 29.7482286], "type": "Point"}, "properties": {"photos": [], "types": ["point_of_interest", "establishment"], "reference": "CmRRAAAAaq3KL11Qdo0dlidziNogQ6MpigoMz8cfFb9HGYClj03Z47vfI1jr6VReEb-rnYeTr0Z66brg6mZLxpKvtfXYrr53Xt5TMP1HFFYw8wCjRCNmeKC4yVO8vGKgltv4mi0MEhAqgZ0n7Uy6ZG66helTv9YkGhT3MWZRBOUrKzn5wJHlKAz00zeVjw", "name": "The Nature Conservancy", "rating": "NA", "id": "90af6fb9fb926dde9f7103577cebc4150bbb1dec", "job_title": "Nextgen-Staffing", "place_id": "ChIJq-m4EX3AQIYRJkn4Lhccp2E", "address": "1800 Augusta Dr #240, Houston, TX 77057, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.42318089999999, 29.7345943], "type": "Point"}, "properties": {"photos": [{"width": 750, "height": 437, "html_attributions": ["<a href=\"https://maps.google.com/maps/contrib/106788706324997826205/photos\">Erika</a>"], "photo_reference": "CoQBdwAAAISit9iqZX9whcYxKF7iTCpnxSgHYXMWjQX5Ch3tmTas26dBQx28OfKmRzxgmBTTuJLGpUp2FkgdlRh01b64xE4-LvaSxnM4wMM_gQAtb9Qe9kdfYD7qKQ3STGFuMG35Ex7OB3L4bWsQmYblsd7fQMSQaayel3niMy_uDCGKcQ1wEhAs7Cna7amRW6KuljRgkmoAGhTCM1ukci4EavJBridJIycGoglGqg"}], "types": ["point_of_interest", "establishment"], "reference": "CmRRAAAA4nl92ceHgD5YxOf4hcvGmSWU8LHqGNQxm41aY2A25oBLwX63bWtRgozMHcwymcC2A10oUTDctfA_SKBCkIJPAiHV6_utPOfoRH4rvZwLIOIx3kOHO5Vneop2bDpDJa9AEhBV-nogga-vllfm-GbuAmWYGhQy135Q-CMODZGRN0DHVxvk0qM9Zg", "name": "Student Conservation Association", "rating": "NA", "id": "1c5ea7722fc0d99e9f7dfca55f5d9078224d51d3", "job_title": "Nextgen-Staffing", "place_id": "ChIJQcqBXfDAQIYRErawO-goGj4", "address": "2990 Richmond Ave Suite #400, Houston, TX 77098, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-96.038102, 30.055621], "type": "Point"}, "properties": {"photos": [{"width": 984, "height": 985, "html_attributions": ["<a href=\"https://maps.google.com/maps/contrib/110279808588468038448/photos\">Peckerwood Garden Conservation Foundation</a>"], "photo_reference": "CoQBdwAAAM4TrE4Jvsk9FXBmofwVvTtTZCqU8ae9F0bb3_Q9YqCOnxL-a4HSKuQHAJPNQ2KgPYh_yRHLZ4rJsbzd2Z0ogrOuDzLV6zHkTK_Zeu9MWBjkMCR19Jo-0DNYF9zLvguINsxbUaagr5c-WubpTxftC71-T-X5Eb_F33Wae8KzOlVYEhBl6vIhK0YdmKnq3a5sttSbGhTW8vf8ci6b25etIEHi9bY74XE9yw"}], "types": ["park", "point_of_interest", "establishment"], "reference": "CmRRAAAA-upk2HI3hxyNEPkxq_kFWbnqXkXhfQf-MDFt7gdlQv2XM-kgAZaGz0RykQl5Wd2z7jO-hMQM2CHugX1EuzMoVAOdAMCoG2wCmfc28Mzf1Lpp4UxgcTvsGjIP4MkwhmPeEhDefksxps36UTE4yoDa9ARcGhSKRTR5fqLw-TRJzaAUNbdXe35WGg", "name": "Peckerwood Garden Conservation Foundation", "rating": "NA", "id": "e618a4c618cd67ce4f5fdc165f640220ab3b53b2", "job_title": "Nextgen-Staffing", "place_id": "ChIJmUR7pvHKRoYRIIl0o73bPGE", "address": "20559 Fm 359 Rd, Pine Island, TX 77445, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.64386449999999, 29.7515036], "type": "Point"}, "properties": {"photos": [], "types": ["point_of_interest", "establishment"], "reference": "CmRRAAAAu2LPFrDKJb6XwdwC8WC9TMaOPCpE3qKisJMc6kYZBwj_jPs0MkCIR-4gnTMmQp_cVWI5snFbuBUgD7eEzcNhaZ-0O9qzdscOxujR2LWkzrDQsOBJGXNeXr4ziZqg6pGjEhBUDGYPiSYQYDR3U5g-9u_JGhRXyztkgi2JV9VwPb0Nn5_3yk8otw", "name": "H2O Conservation Technology", "rating": "NA", "id": "30c07988ef8dfc62dac712b9d587daa4a36f2539", "job_title": "Nextgen-Staffing", "place_id": "ChIJIWZRKeHKQIYRXxta3wOMGGc", "address": "1725 Hwy 6, Houston, TX 77077, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.5705632, 29.7714443], "type": "Point"}, "properties": {"photos": [{"width": 3024, "height": 4032, "html_attributions": ["<a href=\"https://maps.google.com/maps/contrib/108143329814504597326/photos\">State from Jake farm</a>"], "photo_reference": "CoQBdwAAAIy6gLq6xUWa7QrMwqSZ93twMlkMPMHuXiY0fW8h-BKKNvxQnGQmfUPcTfvjwdUXjusVFAyAQDviwZyxogLu4YYoCAEIWudP1BVVLVThikdr45yeircKhKRFXk8BkYd0itmdo365M4lqdkBhyKwPNYybuIEHHvJ_gUUeByoat_9ZEhDJMYlG-J9RUeL4fzzrWWsGGhS2sqcfmPek37fZatCKlYIl6j-xoA"}], "types": ["park", "point_of_interest", "establishment"], "reference": "CmRSAAAATkf4FdrB3n9yOi_els2UVBRsbqPNh9DE72UKd5W9KsA6VipODQU-yx1SiwwJLETS-lETD7lvT0-CXfGYQMH2E4JJ0wYT3Y48iXlc6khm0reHWPlWyprDpZkqY3hAHspFEhCl9lV9-iNJXSr5j5VGVuEjGhRWha06EUOiitcvaq9RKTfX1i9Onw", "name": "Houston Audubon Society", "rating": 5, "id": "050a5458d86bdd1cee7b09678bd6256d0a20a73e", "job_title": "Nextgen-Staffing", "place_id": "ChIJlQOxwVDbQIYR2uX_TZl0TYc", "address": "440 Wilchester Blvd, Houston, TX 77079, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.56820189999999, 29.770778], "type": "Point"}, "properties": {"photos": [{"width": 1800, "height": 1200, "html_attributions": ["<a href=\"https://maps.google.com/maps/contrib/108765250995932379967/photos\">Audubon Docent Guild</a>"], "photo_reference": "CoQBdwAAACqtcdXpOfseJnYhqiCOKedsjtPhWXmxlVONSAWpQqz1w235KlV0ku_uJbqLm2pX6PQKEPaEAv2IyUN3o9A1x971f_iD9b6Vr_mRUlgGItohur6_QRSZq8RoQzhsHAkCLMTxQUrmYXa5oBBZbmuCKjA-DS6NtLrdMDVeaGUaoYJqEhAVli3z9HYH0h7S_UizTQRTGhQ_iP0BS9DjfwgA3I1qNMRu-9bEdQ"}], "types": ["park", "point_of_interest", "establishment"], "reference": "CmRSAAAAKfujWSlfpZApPXMpLmeFvpneCJRnKdcxV3uIYT8iOkeZo5XOOhrxAfIJWsGVEKeCp1Q4fL60Cj8Pt6YubcOmAPRkVMPY2sZnAlNv1DiKJl3ZwTU2zKKcePSfOXqDVHoyEhBwOBVPR7vB_g_lGuDNaTicGhQ-SsunGbpDOXWssAzg8CrXJEa05Q", "name": "Audubon Docent Guild", "rating": 5, "id": "7ddd5daf76cc4979e2ba6b062322d1c77d5d1c07", "job_title": "Nextgen-Staffing", "place_id": "ChIJI9XyNFHbQIYRtwHb8EtTpeU", "address": "440 Wilchester Blvd, Houston, TX 77079, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.44932349999999, 29.7803218], "type": "Point"}, "properties": {"photos": [], "types": ["point_of_interest", "establishment"], "reference": "CmRSAAAAoS-y-rBKQ_TBwd2YdNyTWMWEkA7UKH_KRXIUnYyY1IquVAwz2rmxtkZKzByRNrRhY4v2dYwE6MSjzDSJ4aPZQbAJ_rjtF34bBIdq1XWQkjuFm_kIw7CSUDH1kpNlvE1aEhDhKfObj6jSCd3r9e68CvtyGhTTWbitcX3ANVX52Ym4DX_Mky3TIw", "name": "Coastal Conservation Association-Tx", "rating": 3, "id": "7258b034e119f31e82320bca6e72781ee9f79d75", "job_title": "Macy%27s", "place_id": "ChIJcekacM_GQIYRPzL13cgQrPk", "address": "6919 Portwest Dr #100, Houston, TX 77024, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.47039, 29.655454], "type": "Point"}, "properties": {"photos": [{"width": 5312, "height": 2988, "html_attributions": ["<a href=\"https://maps.google.com/maps/contrib/101184977609161362375/photos\">aug4</a>"], "photo_reference": "CoQBdwAAAC6hgVkcuU03OxQpB2CPf9FOgn2jF1-l0i9OOLFX61HDRH1sXm2xxkl75oteZaajLRfPvw97u6YrvSGK3X4ZnkbmVnjmpwlwJhmK_Hj7mCRDtbP7mx3zEBK43TZ_UPkRM4sdsjtviySFwXOEH2iTUdsoH4XUNfePXMplCtepT1bXEhAA567xU6yF1NXJn1x4qahGGhQFScrPntu7Lt1BZLduiHoD-Mpnvg"}], "types": ["park", "point_of_interest", "establishment"], "reference": "CmRRAAAA8c-BpSnxJRV5VEOYrQMahLj5z77-2N06uR0adEBq1Hakvcr_wyHDVnjqWPp1VEh50PPWzmGypWc8ajfSY6r5Wnffddxj34SwGWyFUZ9FTjoMF0xuwlGB3Cu45jAZgegLEhD42BNl_voBmQJYHwqGrSLvGhTiB9WDF0veKpTNdRt1E_OeUGJkPQ", "name": "Willow Waterhole Greenspace", "rating": 4.3, "id": "0127506e8071350c2d48f0ca56e939045297a0f4", "job_title": "Macy%27s", "place_id": "ChIJR6_2zTzqQIYRsA7wExgfDWs", "address": "S Willow Dr, Houston, TX 77035, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.4003322, 29.7388505], "type": "Point"}, "properties": {"photos": [{"width": 1136, "height": 640, "html_attributions": ["<a href=\"https://maps.google.com/maps/contrib/117056878997299689379/photos\">Marisol Brown</a>"], "photo_reference": "CoQBdwAAAExZd5z8CSqoqnxnMgCzQ4zruiP3dPqeBGlwh9jTTOGYhRBfl7HmO8iSLGBoJIxMISZaim1Q5f93Gd3-Gnw1W9s8PPhoVsW5BWPMfVydWdw4QhNj3Qr67HtYTiOrjEWlDSKIGqcPuMN-gM-AYWhtnuw5uuI0GqNspnUR3-amHQLnEhCjqMz4uz3ry5nhpED8RJF5GhRdGLTIXPVVjau0OR55EHkq2j1Ujw"}], "types": ["point_of_interest", "establishment"], "reference": "CmRRAAAARwICExyyEhl2FDNxx6AeFRorB0U0bHoiGr8SbKLUU9zC3bwTP_wSXonwoGb5N4n0a6XALaDD34n9fNo2nLnH5N24tX0U6Hm7w_0dRkx-aYbl6vO8Eo4KLYBjYhCLK5grEhBbSAx3J0gE2aumOEqfPEdMGhT5AYTvjekz1_ulfUc658JUsy-UPg", "name": "Masters Fine Art Conservation", "rating": 5, "id": "a462c2eef4e22ea319485ae7b84f3d20756cbdd1", "job_title": "Macy%27s", "place_id": "ChIJp8u2bZvAQIYRbosnWz6cVmY", "address": "1612 W Alabama St, Houston, TX 77006, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.3876169, 29.794149], "type": "Point"}, "properties": {"photos": [], "types": ["art_gallery", "point_of_interest", "establishment"], "reference": "CmRRAAAAMNAqlSesbWS6h7OMdb7_nmAEwIV96XDKrjIrvBf18vhdAuXlURvX29fgOfKqnCKR7hiArdC0HrEqa97G9gkQN9ADhwaNW2NLGHkltuN_rGya8UU_E3Fn6jN6aFnBDjXGEhDefjmbR6C0zVkLT-ujaJYnGhQ44_ULQS8AwrylRWKPrqxZ7Qct5g", "name": "Whitten & Proctor Fine Art Conservation", "rating": "NA", "id": "883a8c5ef35ab28e1630235ad65a6b16506a67fa", "job_title": "Macy%27s", "place_id": "ChIJ8YuXE6K4QIYRn1SF1hazFEw", "address": "1236 Studewood St, Houston, TX 77008, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.3858767, 29.7300997], "type": "Point"}, "properties": {"photos": [], "types": ["point_of_interest", "establishment"], "reference": "CmRSAAAAnzb70aoQvdt08GAKr9KIRbWvIivQNMZuVnTLgpb4SqfThxUuex-TtCszfCdMeQtQV02MBXjj2dDDOxM2itM9E0zirxPLB3SRXfRWnBkaYaKJdhkqOXCCGllhbTZFfV4cEhCXOyYje4Fw5zfxxIvGfHWbGhQUlUhr1r2fVpGmuTsUPM8x7TbRnA", "name": "St Mark Fine Arts Conservation", "rating": 5, "id": "ea2d4bac6d74716b33f456dff3aae0cc0b43cca3", "job_title": "Macy%27s", "place_id": "ChIJKbDEoXm_QIYRcRFBlp0dE8A", "address": "4901 Main St, Houston, TX 77002, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.483218, 29.7482286], "type": "Point"}, "properties": {"photos": [], "types": ["point_of_interest", "establishment"], "reference": "CmRRAAAA7HDcOPGpFuwq-WVgHbk5SYApjowSfiThlvQYoUXD9cq6Aqpq0Lz2faQQKuYhj0M3cpOrVrKwP-2KniJhXiRMxiRHgaOEleoMzjIM7MDzVT3gIkT2Fq034N6-oiAUpAu5EhDkZWK8K_eGLIXOYEIOgSEIGhS0JCNR6OATl9W1N2mOoDHDqXujvQ", "name": "The Nature Conservancy", "rating": "NA", "id": "90af6fb9fb926dde9f7103577cebc4150bbb1dec", "job_title": "Macy%27s", "place_id": "ChIJq-m4EX3AQIYRJkn4Lhccp2E", "address": "1800 Augusta Dr #240, Houston, TX 77057, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.42318089999999, 29.7345943], "type": "Point"}, "properties": {"photos": [{"width": 750, "height": 437, "html_attributions": ["<a href=\"https://maps.google.com/maps/contrib/106788706324997826205/photos\">Erika</a>"], "photo_reference": "CoQBdwAAAKTZaDz6Y5p9XROexiw7TlA2enPh2iDYBEGsJIB7nvtCkinE-jOoiIdfNpaKpeYxCiO4GMpS3UKjMh_p7P7nuDtcXpI0_jO-mVqf9E1YVbDvQ6x40lMewrMWZytjfyM5eO178SwuSKoVfRTty4Z6H0Uzx86rdrgnT1QtOZTajpSWEhAnnaZNmMKbVsiIyLwusHpWGhSpxtbE0Ncke1BUBzjU1zbDBBOWzw"}], "types": ["point_of_interest", "establishment"], "reference": "CmRRAAAAr-1-kETFqUOtJxNVxeTUyaRb_Vj0TBNHRxrXtFNjc_NU9OvhxNHmBV5eBMcCKIJuXyfZ1HQ-h83uABtzZN9n1FG9DeNNr4GQbNhPxSyZxJOg24IYQEzOOYHXY6iVipI7EhAdqJoLI9-pkckZMnV8WZ2yGhRisvbNJwcxYZS05Ahon4K9XgW0kg", "name": "Student Conservation Association", "rating": "NA", "id": "1c5ea7722fc0d99e9f7dfca55f5d9078224d51d3", "job_title": "Macy%27s", "place_id": "ChIJQcqBXfDAQIYRErawO-goGj4", "address": "2990 Richmond Ave Suite #400, Houston, TX 77098, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-96.038102, 30.055621], "type": "Point"}, "properties": {"photos": [{"width": 984, "height": 985, "html_attributions": ["<a href=\"https://maps.google.com/maps/contrib/110279808588468038448/photos\">Peckerwood Garden Conservation Foundation</a>"], "photo_reference": "CoQBdwAAALvw1_PIwuo7ekMxt3SUsFyPv7v6s-18z4L9OfcJxEDHYmKochoIqtt_GCYf15FTiWjI4Z0QMLvRxu90GX9IRiCAgEbvqdrGsHfMSHxM9etgTTa6SPVkMz2Iu_96OBl69WAen3XhyazvjL-a9lT9d0FZPnjCQMUGC3KSgT-FrjJ1EhBa7dTsiLWhzTztQW6cQBscGhR_jyJ4ZUiDkb4p7AMpNZR9Hx9GSQ"}], "types": ["park", "point_of_interest", "establishment"], "reference": "CmRRAAAA3GRixOLQeg03ZO2Rghz9apiZ2zonEvQfTe5VNEra478RF8AONBgIAS123vlP-TV0JTyq9CeX0ZJRgHVE69QCFhsYjBXolZtcNSWAR_wXLIysPJMK1k-eZqTBFemSKv76EhB7ptfo_KOD7j8QjgtBWwbsGhSwhePCNbqP_WVpgKmtZ4-YJ56nBg", "name": "Peckerwood Garden Conservation Foundation", "rating": "NA", "id": "e618a4c618cd67ce4f5fdc165f640220ab3b53b2", "job_title": "Macy%27s", "place_id": "ChIJmUR7pvHKRoYRIIl0o73bPGE", "address": "20559 Fm 359 Rd, Pine Island, TX 77445, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.64386449999999, 29.7515036], "type": "Point"}, "properties": {"photos": [], "types": ["point_of_interest", "establishment"], "reference": "CmRRAAAAfecwJsFIrKo2ca7tYIci7nKzDT9RUuEhaYlg8la5d6BN42qopf2nlkSfzAHhzxeoJjT4fGm8yr-L-TX9cO5ZxNU3MvRtR_Zp2aNvx-LdF03PtlrxZF9pvFjOamgHW3w9EhBW55GTK3Jk1u5qyJpCL8zIGhTts0U5P65MGVouMPsKIMHXBoTxng", "name": "H2O Conservation Technology", "rating": "NA", "id": "30c07988ef8dfc62dac712b9d587daa4a36f2539", "job_title": "Macy%27s", "place_id": "ChIJIWZRKeHKQIYRXxta3wOMGGc", "address": "1725 Hwy 6, Houston, TX 77077, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.5705632, 29.7714443], "type": "Point"}, "properties": {"photos": [{"width": 3024, "height": 4032, "html_attributions": ["<a href=\"https://maps.google.com/maps/contrib/108143329814504597326/photos\">State from Jake farm</a>"], "photo_reference": "CoQBdwAAAJEJ64hCoLbiairoMfQjrgVQ4R_U4aP1U27-ASo2YezNMnJjcWdnrioZ2CCCZzJItg1m6S3CrWcnS_guTzz8hN5OMeEfsfwFv-0M33z2rs6ytan4iHXMyHbJo0ssdb19N9I7vf8dmQPuY6YWGF4M1lQuJ5ON7KgQzeC8YctrtQTaEhAxj4d2A_nc_r7McHA477yMGhSx0erpbBy8z1R0myJxwCsX7QFRUQ"}], "types": ["park", "point_of_interest", "establishment"], "reference": "CmRSAAAAd9SF8bnZxFunPltgeXPwKzWrBzklHboMUiDAPJeKRy9J4Ykp1JcP3q41CZ587iWs8l0nvZOHU6PYlpvGpX2bZjd1cbsRfpjBDsWu-3JS0RO2RsI0319hrRUx7oYXz3FYEhCA4ayJxKHmGez2PlKQeobwGhRlF9TzEt2uDhc-JtR0eLDo4VafPQ", "name": "Houston Audubon Society", "rating": 5, "id": "050a5458d86bdd1cee7b09678bd6256d0a20a73e", "job_title": "Macy%27s", "place_id": "ChIJlQOxwVDbQIYR2uX_TZl0TYc", "address": "440 Wilchester Blvd, Houston, TX 77079, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.56820189999999, 29.770778], "type": "Point"}, "properties": {"photos": [{"width": 1800, "height": 1200, "html_attributions": ["<a href=\"https://maps.google.com/maps/contrib/108765250995932379967/photos\">Audubon Docent Guild</a>"], "photo_reference": "CoQBdwAAAATdfTyMFdrxZ9nqbQQ3bG3_Jc3k28yuPDOptvAGk83gS5UZjS8_pUqviRwhiWCVNRH2EhmbwDa0QFyQdJWgFV12YO0s-NoA1OSO28_X8bimxNpQzQrLEx16cTC9kshDlYNVw31GA_N2GuqRtMPgg9KxM7EVJU_gueQs5wIRAq0JEhCJEQHDhyAKjKbSRJG9Uh0KGhQUDRMzoxNfYN88SJH6I5PdXS5r7Q"}], "types": ["park", "point_of_interest", "establishment"], "reference": "CmRSAAAApj7a-_gvpyTa59XUNRN4ZQ-H44lkyGBSpzSzfsNRlRl8GoMv8NyJthORPXk9FALQnSa5P8Ee6tcHWLobOgbvika0PKNLCl-puVIAnj0_eyotiW4ISK0S9SWOkuJe2fh3EhCQQNyp6TYUkyahWJJAjbS1GhS_x0PNz9PPNGsIVbhwUkgRasCzKA", "name": "Audubon Docent Guild", "rating": 5, "id": "7ddd5daf76cc4979e2ba6b062322d1c77d5d1c07", "job_title": "Macy%27s", "place_id": "ChIJI9XyNFHbQIYRtwHb8EtTpeU", "address": "440 Wilchester Blvd, Houston, TX 77079, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.44932349999999, 29.7803218], "type": "Point"}, "properties": {"photos": [], "types": ["point_of_interest", "establishment"], "reference": "CmRSAAAANRSQ3cjSY3rRQMqSyChYBT19oOi2jSnGAGfKiJnUcN22fP6Og_1yIbargfEQRjAcNXOjne_ppih5hcpEPIfWTigjM0eh8F1UPA4Ta0-uoeHfJaI0TGn4uUuwQ1gApcTQEhBCDbud_8hpXtBk5AApl7tzGhQC0CpEWO0JhnShMIu1YicgDhPzcQ", "name": "Coastal Conservation Association-Tx", "rating": 3, "id": "7258b034e119f31e82320bca6e72781ee9f79d75", "job_title": "Nalco-Champion%2C-An-Ecolab-Company", "place_id": "ChIJcekacM_GQIYRPzL13cgQrPk", "address": "6919 Portwest Dr #100, Houston, TX 77024, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.47039, 29.655454], "type": "Point"}, "properties": {"photos": [{"width": 5312, "height": 2988, "html_attributions": ["<a href=\"https://maps.google.com/maps/contrib/101184977609161362375/photos\">aug4</a>"], "photo_reference": "CoQBdwAAAK5wC6cqlJRzO-tVpVDWDY048pX3DPwX1oqV8vLnHCjJxj1yGjmuhDL7HFXeN4CeOVCoOhpEVtId4W_nnnmNFy3r4IEuH7erNH8ENDeR0yc_o2Ky2vn4WEtxe9Fa_UPe0-IkFMILrDYWxsP3VTYHn2FIzHAsd_Agq06CnxC2p5JtEhBDt59D3cHWA01DQqjyTjT2GhRnFRXjWu4B-BrqrrgOl9Mtl2JROA"}], "types": ["park", "point_of_interest", "establishment"], "reference": "CmRRAAAA9PkMEWhQgZXg9KRcCNQbSe7ol7gNCi5LFLvE-qeirESvh82KU5QRM6qa5WMn8zV35_0OVV4Wjg2UFk8A7JUvrpcLZljxLslQmvK_LBBRJEOnl47deCni9GdNLQNPaiUFEhD6bLHM_lA1AnW5AkbAm2JUGhTWGs50-dnXyB4bsmU1HmjRigVmQw", "name": "Willow Waterhole Greenspace", "rating": 4.3, "id": "0127506e8071350c2d48f0ca56e939045297a0f4", "job_title": "Nalco-Champion%2C-An-Ecolab-Company", "place_id": "ChIJR6_2zTzqQIYRsA7wExgfDWs", "address": "S Willow Dr, Houston, TX 77035, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.4003322, 29.7388505], "type": "Point"}, "properties": {"photos": [{"width": 1136, "height": 640, "html_attributions": ["<a href=\"https://maps.google.com/maps/contrib/117056878997299689379/photos\">Marisol Brown</a>"], "photo_reference": "CoQBdwAAADVLdpvSqTxkvKziDf3X9uz-e3PUkIEOqBFCLPcI_k4ETiYNTNGEhQcZKyymXliZV6Px3Y2OAXoJkEDYEdrDlDfxs1eCKPoydnYMjLgFz17lYxNnRo3dmWf0ayYI1PohqWHWQ92w_bUnFokpFM98iaVTYNBMJteddVwy5o-hT_kREhBrJyTR3NlHZ29NIiDwg9tRGhSIiRz9yK5bPBUBXQ27_rs3WeM0cg"}], "types": ["point_of_interest", "establishment"], "reference": "CmRRAAAAX9oJzn0qAn_5C-4_7gcFtrYQY5wKgkcq4JKbZKItKxJcNl3wmUZPPaNEJA2v7mCRN9CtlBWc4GK67-cQg1HyfIPB6ShWlyOufhHQqjMVMAd6t5a_X4Cx6UP5U5lQplUdEhCB3_8dVCgLyVODlKvbwBTnGhQ_rJap0cKmyFWmZVjPJFvD47MfZw", "name": "Masters Fine Art Conservation", "rating": 5, "id": "a462c2eef4e22ea319485ae7b84f3d20756cbdd1", "job_title": "Nalco-Champion%2C-An-Ecolab-Company", "place_id": "ChIJp8u2bZvAQIYRbosnWz6cVmY", "address": "1612 W Alabama St, Houston, TX 77006, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.3876169, 29.794149], "type": "Point"}, "properties": {"photos": [], "types": ["art_gallery", "point_of_interest", "establishment"], "reference": "CmRRAAAAj5l_GaPfi5Z4W2gBVd9gCELwYbuY9inx_9Fj4DLrsYpgnfAxFSErmiwfjCwKZyDNeFkx3MC7pf6twGsFNR3YPjHNbNDZxRRQDPF--qHu1CXecbLZQgwyXt7S49fmwa-JEhC0LpUt0o4AYwNGkyicPkI4GhRywmZYE_59LRoN7t1ynilUweJlvQ", "name": "Whitten & Proctor Fine Art Conservation", "rating": "NA", "id": "883a8c5ef35ab28e1630235ad65a6b16506a67fa", "job_title": "Nalco-Champion%2C-An-Ecolab-Company", "place_id": "ChIJ8YuXE6K4QIYRn1SF1hazFEw", "address": "1236 Studewood St, Houston, TX 77008, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.3858767, 29.7300997], "type": "Point"}, "properties": {"photos": [], "types": ["point_of_interest", "establishment"], "reference": "CmRSAAAAJ5Z-C3RWshw8F-6oJ96VGEMlC5dj6-8siEDPyGr1ccbQf4OD_eUNiRZK5TW4JR7k2-oNlEusEFbiX2naWUPR1pYqKPn3UPCDwdRj3fP_W-xpJevRZL8NDFZ_P-8qXBLpEhCdFDKDx3BvNjcgEwnf3OReGhTGU1R000vjWOrLtRwJ-zWEeeXxIA", "name": "St Mark Fine Arts Conservation", "rating": 5, "id": "ea2d4bac6d74716b33f456dff3aae0cc0b43cca3", "job_title": "Nalco-Champion%2C-An-Ecolab-Company", "place_id": "ChIJKbDEoXm_QIYRcRFBlp0dE8A", "address": "4901 Main St, Houston, TX 77002, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.483218, 29.7482286], "type": "Point"}, "properties": {"photos": [], "types": ["point_of_interest", "establishment"], "reference": "CmRRAAAAtUOHKlMFWCUbEzOHfIHO10SLFO0fRcrN56ywlTzmJZF8DHsn_yfU5VS0nHDMvRUc32jhK8Nw62azgrMZr2mG5bteW2CicaS80lIo67ZkyPibqqos7Fh_93M3dmuSwEtZEhAbD5e_eA2T2Kt2G51RB1AKGhQt112ow0Re19J-f7xA9pSVZnYgyg", "name": "The Nature Conservancy", "rating": "NA", "id": "90af6fb9fb926dde9f7103577cebc4150bbb1dec", "job_title": "Nalco-Champion%2C-An-Ecolab-Company", "place_id": "ChIJq-m4EX3AQIYRJkn4Lhccp2E", "address": "1800 Augusta Dr #240, Houston, TX 77057, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.42318089999999, 29.7345943], "type": "Point"}, "properties": {"photos": [{"width": 750, "height": 437, "html_attributions": ["<a href=\"https://maps.google.com/maps/contrib/106788706324997826205/photos\">Erika</a>"], "photo_reference": "CoQBdwAAAMlAzBVbTqq0nkQCs3KF-OO6HZyIyKKKXs2Y7yGM0EOyT0sriMPIWL2HPsCSOOWIJF5A51XiLFl5LjbZf0PTYo6aVk8V9KDqZGNL3O5gWtikWv09_xgvtSaAwCzs5qxHbozaNR3bEcNMRxeZ6hWC-abbeDQkIOallehKx2EpdxmYEhABYT0O-mhIPF4cDJ5_Jc1QGhQf3iwU_7ev5ej1DdZDreqpvZpo6g"}], "types": ["point_of_interest", "establishment"], "reference": "CmRRAAAAgl56rOwWrrb5SPpm7x-YE-jP1_qv8LdWTm832RUFP8V448vAt0qXRZi5l1FWrP2zqpa3Dtw5Iu-wW9Np6za6npTf1614a6q2-g2FL5BanSXh_H2EYKjrsQUBBV8jx4NlEhBKS1Na5u80ESk9P22_T95OGhTq1vveSkFDuFDDqp6yiiasp8jShw", "name": "Student Conservation Association", "rating": "NA", "id": "1c5ea7722fc0d99e9f7dfca55f5d9078224d51d3", "job_title": "Nalco-Champion%2C-An-Ecolab-Company", "place_id": "ChIJQcqBXfDAQIYRErawO-goGj4", "address": "2990 Richmond Ave Suite #400, Houston, TX 77098, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-96.038102, 30.055621], "type": "Point"}, "properties": {"photos": [{"width": 984, "height": 985, "html_attributions": ["<a href=\"https://maps.google.com/maps/contrib/110279808588468038448/photos\">Peckerwood Garden Conservation Foundation</a>"], "photo_reference": "CoQBdwAAAE8i3YHXMYoRZ_ANjC_pLj0PEUmkKLKnyQ45P_nm0qDZH65SctRxTu75nABIyz8wxo0QxQQirXWXsqW15DbmCbrFMd-uEI6X3L6D832ac_bi9fVISs-F9B4nqlhvg8LAZ3heVgKn78syYsauER_IyR2kCzOZ9s9C4q_mkdyuqHeFEhA4no4wbll4pr0f8D4NHSO_GhRbFeovx9wYnJZGUZQvjY33yadydw"}], "types": ["park", "point_of_interest", "establishment"], "reference": "CmRRAAAArq6rSrCX2a9069ErywivyppwQltcQZ5pWYczedqaHqj2YuyhmlqASnvNId2oTwMUtTpF9oShjpHh3ysCkmcP_58BG8fDfrP4P-FZxqPi6EydFosN5hPMB_po2PkIRrXUEhAcG_rVLdvwhx2jciMrABGrGhQcZ2AB1cUSpVlvntmrCb29CgACZQ", "name": "Peckerwood Garden Conservation Foundation", "rating": "NA", "id": "e618a4c618cd67ce4f5fdc165f640220ab3b53b2", "job_title": "Nalco-Champion%2C-An-Ecolab-Company", "place_id": "ChIJmUR7pvHKRoYRIIl0o73bPGE", "address": "20559 Fm 359 Rd, Pine Island, TX 77445, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.64386449999999, 29.7515036], "type": "Point"}, "properties": {"photos": [], "types": ["point_of_interest", "establishment"], "reference": "CmRRAAAA9yzvYK5a-5utnHxvlj2_SdHHD-wqVoQgRfpiCeG-rhfAsurbG5ltEtuUqsnFQJwDpeaQStQ5Kzgnc8SYBRHdIdqJ65z-ygedF3vEMMnaHSRD6uM_Q0WUVQ6DY5C6exngEhAGr40LfpQjo8RGPkFeOjiBGhQwYqEoHXfhDy643zwWl7TqvFOHKA", "name": "H2O Conservation Technology", "rating": "NA", "id": "30c07988ef8dfc62dac712b9d587daa4a36f2539", "job_title": "Nalco-Champion%2C-An-Ecolab-Company", "place_id": "ChIJIWZRKeHKQIYRXxta3wOMGGc", "address": "1725 Hwy 6, Houston, TX 77077, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.5705632, 29.7714443], "type": "Point"}, "properties": {"photos": [{"width": 3024, "height": 4032, "html_attributions": ["<a href=\"https://maps.google.com/maps/contrib/108143329814504597326/photos\">State from Jake farm</a>"], "photo_reference": "CoQBdwAAADgsq8RLFkUylBeaus6l9ztHjYtnfdgBbNu1Fm8P68OREZHwCDHKOsCVwX02llWmWoIf54SXYM5h8t4x34MhFeGIZsRk6YP1MWQtHe1NqgMxqSLbaV5GNlwJigwUy-Rh3f5wBHfj21nqvX6CwLCQv0uYb3-eLf45GaFVBCW7muBiEhDQsaRAm9fWDAmQKgmp2caJGhR0zQa7v4bqOX9mhauvWz9mWbmKSg"}], "types": ["park", "point_of_interest", "establishment"], "reference": "CmRSAAAAxLruHMkS9bKVU1yhszxzwES7ZgGr-q0CVy2yXtQMqQIc_TRoByzrTCpWTXWUDD2vhsYxd_MSo408Qm3A2Spu9csxdvm67okMJ9kcVRyFDdC56Mfc6s-HFuJHaRfERlY-EhDc4a926xb1PtSGcNo29ugUGhQuGJUv0w3YE1t_x2iBIqZ6I02Y-w", "name": "Houston Audubon Society", "rating": 5, "id": "050a5458d86bdd1cee7b09678bd6256d0a20a73e", "job_title": "Nalco-Champion%2C-An-Ecolab-Company", "place_id": "ChIJlQOxwVDbQIYR2uX_TZl0TYc", "address": "440 Wilchester Blvd, Houston, TX 77079, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.56820189999999, 29.770778], "type": "Point"}, "properties": {"photos": [{"width": 1800, "height": 1200, "html_attributions": ["<a href=\"https://maps.google.com/maps/contrib/108765250995932379967/photos\">Audubon Docent Guild</a>"], "photo_reference": "CoQBdwAAAPPdR_lngrYG97fmAnCBtbB6pW6BR9cfkRLYyYY6Ci8xiRiaOAwrkxCx9HMW_2OefBVvFD6o-uRhmPwQaoOS1PKdpEG3tiMDK6Lm8h_aAs-yX8qwS1P69AwJawqfiLdZpoTgKKG9tZtXUFhQubzSH3yXwwGpBkmxGOMn7u7nL8XEEhB0ieVtOXYKijOcsazYkrRTGhSIqYfYvmomHqgN0bUHBD1c2v9xgw"}], "types": ["park", "point_of_interest", "establishment"], "reference": "CmRSAAAAyh3tykJ5-AQiRKrKBziMhL9KjTby1befjF2h2mcLHx0KKt1IJAPOiE3k_1dBc6y-efZ9S_JrAHbwx9V5CmaNDsEWcCGQOnd3lC0QlzpacWvTAWF7-AqZu__7PTO5lhstEhAvbxzJQE_QFYnQTaJGlgthGhT29vBv5G8-VQ40Vp6lWTNvlMuwww", "name": "Audubon Docent Guild", "rating": 5, "id": "7ddd5daf76cc4979e2ba6b062322d1c77d5d1c07", "job_title": "Nalco-Champion%2C-An-Ecolab-Company", "place_id": "ChIJI9XyNFHbQIYRtwHb8EtTpeU", "address": "440 Wilchester Blvd, Houston, TX 77079, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.44932349999999, 29.7803218], "type": "Point"}, "properties": {"photos": [], "types": ["point_of_interest", "establishment"], "reference": "CmRSAAAA8seT8-hLpqol9HnvhYZlnb65xUIXj8c7LS87jdYnIQivU7Wu48fusCjJ_moAfntqVU4ayvJuxSGyIQOOcHrdvfbuXkckJNJ1v00f5Qsfu0SWft6IYxifYtvtFp1vPHLYEhBfCQnAY6HGyiwpyo0EJXdcGhS3Jphzo3XPI3TPGLctat4OnwP6Jw", "name": "Coastal Conservation Association-Tx", "rating": 3, "id": "7258b034e119f31e82320bca6e72781ee9f79d75", "job_title": "Ranger-6b982a83", "place_id": "ChIJcekacM_GQIYRPzL13cgQrPk", "address": "6919 Portwest Dr #100, Houston, TX 77024, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.47039, 29.655454], "type": "Point"}, "properties": {"photos": [{"width": 5312, "height": 2988, "html_attributions": ["<a href=\"https://maps.google.com/maps/contrib/101184977609161362375/photos\">aug4</a>"], "photo_reference": "CoQBdwAAAE6ksyM50TeJO5iiaEfOg3C-q2xmnH9PZmMD1SET_xZBZ9h2CW0s_xCpXM2TMhN8xCvn_7lH4kmHNELYVc0FGfLJ-UBPhSSUah95aUE7bwMwsQCxGy0ceNwFNq0_SMDoD6gQyJuMHLUZ1npbRmba2Gta2ZUGkKiwaZW1hB9O6EJoEhCoe8ECLdG5hj_Uor8AN07tGhT7ZaClph25J0SQ632682x0VyTvnw"}], "types": ["park", "point_of_interest", "establishment"], "reference": "CmRRAAAAODgUgPycWVHeXZKB80RSAmFVWIKBsQcR4YrdEVQV-wMMvtUDsLCtn6uf3WosN92c-Cy0kf2c03-U5-jZiIHjuRoowSd7aQcHQ23Gg6rtf7_A55DxEPtE6jhIATOPIMOWEhBsj9N3-lIOi6Nm4CZmpmgRGhSicnZYYkNmgMGW9-unMKLryuJ_Yw", "name": "Willow Waterhole Greenspace", "rating": 4.3, "id": "0127506e8071350c2d48f0ca56e939045297a0f4", "job_title": "Ranger-6b982a83", "place_id": "ChIJR6_2zTzqQIYRsA7wExgfDWs", "address": "S Willow Dr, Houston, TX 77035, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.4003322, 29.7388505], "type": "Point"}, "properties": {"photos": [{"width": 1136, "height": 640, "html_attributions": ["<a href=\"https://maps.google.com/maps/contrib/117056878997299689379/photos\">Marisol Brown</a>"], "photo_reference": "CoQBdwAAAPOkOEpMbzBL5wKPNcPM9i_D1YU1sYTfGEHVMgcp-1MtzdARj_9c6gPVM2uSdsStdeQSUK9gC-Rv52zlFLF1F2xTIMGa3hQ2pd6r6fYoz23-SzjYRUCznf-5vj8GKdJR4QCQvJIocC8h_PQR3N1k26R5Br3Rn1JWS5xVpm4RtVzFEhBJJw6uBYLS2ykMFQAwpmIGGhQl3PABwbZcBnRSSEOiprvpkqkGDg"}], "types": ["point_of_interest", "establishment"], "reference": "CmRRAAAAK5dyfkLnGZ_ieVmdIwPN3ajh3TmB-mgu_285Ru9E7zstxSu35QV6bbKuq2Cqf5HfmzJBtnaDsEklV0-2ZvcBlIoM3ZTvRo18BC2aO47NH4w9S1vhTqiKE3TlWKiWAJR6EhAbEKRbIov3wr6DkrB3EL4CGhRmQK5N8GEGLB3sfKAvXDKf2cY_0A", "name": "Masters Fine Art Conservation", "rating": 5, "id": "a462c2eef4e22ea319485ae7b84f3d20756cbdd1", "job_title": "Ranger-6b982a83", "place_id": "ChIJp8u2bZvAQIYRbosnWz6cVmY", "address": "1612 W Alabama St, Houston, TX 77006, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.3876169, 29.794149], "type": "Point"}, "properties": {"photos": [], "types": ["art_gallery", "point_of_interest", "establishment"], "reference": "CmRRAAAAotlD0FOU5CTKVuSJyWhx4z_s4HKdTT3R43F_pOHgUHnOTvcT_bj4rC8o0NY63MJcZBztAAd5RUPdPsfpzVoNnUaniH-Rf4v9k2Fpmz60XuAhuEsKcQhMq7OVzyKlpyDUEhA9MK1uXn9iPmxJ_1Gz55eEGhQsxW0YHWcVQWzSoo5kz9d_uJyBAg", "name": "Whitten & Proctor Fine Art Conservation", "rating": "NA", "id": "883a8c5ef35ab28e1630235ad65a6b16506a67fa", "job_title": "Ranger-6b982a83", "place_id": "ChIJ8YuXE6K4QIYRn1SF1hazFEw", "address": "1236 Studewood St, Houston, TX 77008, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.3858767, 29.7300997], "type": "Point"}, "properties": {"photos": [], "types": ["point_of_interest", "establishment"], "reference": "CmRSAAAAzgFvT0bv5p5ZU22yHLVvzN6VOesaX8KpljL0AwO3XjGhzdMF282ieD2pK2Yj9Ts6knJkHa2oLveEH9T7DGhyW6yJZ9lwb52G7Aj_wE02uHaxcLN6GvOUlcf_ICYzfuZIEhAsafJwNIEMMtzr_n_5JR12GhSp8HuSGhP3wVpw3ftw8qYc0PHogw", "name": "St Mark Fine Arts Conservation", "rating": 5, "id": "ea2d4bac6d74716b33f456dff3aae0cc0b43cca3", "job_title": "Ranger-6b982a83", "place_id": "ChIJKbDEoXm_QIYRcRFBlp0dE8A", "address": "4901 Main St, Houston, TX 77002, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.483218, 29.7482286], "type": "Point"}, "properties": {"photos": [], "types": ["point_of_interest", "establishment"], "reference": "CmRRAAAASl4L7a0fHkAIQSweRqeNNptG0iPk-DKkHtlGJssnTmVXMwNwhswJxm6TvBv7QAkrRdFJBPAcBPB-Ejz7rB7hsMoNmY1pVeiTyL7YWVXc4GgoArOUmyGbSM7vi9OPVwQtEhB4_PNDoH9QLjliicP8di8nGhSj27QKOoN-dffOF3Les-9XghfrWA", "name": "The Nature Conservancy", "rating": "NA", "id": "90af6fb9fb926dde9f7103577cebc4150bbb1dec", "job_title": "Ranger-6b982a83", "place_id": "ChIJq-m4EX3AQIYRJkn4Lhccp2E", "address": "1800 Augusta Dr #240, Houston, TX 77057, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.42318089999999, 29.7345943], "type": "Point"}, "properties": {"photos": [{"width": 750, "height": 437, "html_attributions": ["<a href=\"https://maps.google.com/maps/contrib/106788706324997826205/photos\">Erika</a>"], "photo_reference": "CoQBdwAAAI0HIorSUM2MT0iU6cyorY-RzdmCTO6MxZHGKlTgLqvZ8rScZ9Sg-IqPWfEzuzK4LqVMA7A6AEuvaDUNL9bBB1u_VyF8lVP4Ynq53Y0o6ZbQ_-XtU9pgWvbWR-N6Lo9xHW4iQW51eIdA1hboo6wHDF4kTXTyx6LVm9rIz74UMKp9EhARVVcDw9yn1FG4-ngHUsJ9GhQyy0q2-nmyYAGSzpcF7wAyedroPA"}], "types": ["point_of_interest", "establishment"], "reference": "CmRRAAAAv_awIHf-gKoim1nuToNKp54LpgkVmrYcxrvyQ8LJw4rekEts07S4bdiF-qvgLBZnUkiilGhRA8FwE1HjQ4CXfYYKM1sQxt0VXfxGvz4ykDsRfsGqhhEgbYldgHVnybdGEhBiO8l_Yb6pLueoBwwEC4klGhTU9BnZ1WOrxP0a9cTpyBbpX4yDKQ", "name": "Student Conservation Association", "rating": "NA", "id": "1c5ea7722fc0d99e9f7dfca55f5d9078224d51d3", "job_title": "Ranger-6b982a83", "place_id": "ChIJQcqBXfDAQIYRErawO-goGj4", "address": "2990 Richmond Ave Suite #400, Houston, TX 77098, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-96.038102, 30.055621], "type": "Point"}, "properties": {"photos": [{"width": 984, "height": 985, "html_attributions": ["<a href=\"https://maps.google.com/maps/contrib/110279808588468038448/photos\">Peckerwood Garden Conservation Foundation</a>"], "photo_reference": "CoQBdwAAAC2MT_Rj7DLvd-WWGiyOMngiMc6hnxIJOnn9tjQmfvKMEOVJAmTRaENSfnw-RJyo4aFYv79Z9sNo-c4t5XqSrWRLICH0eUA9bQ_UY8eyRdT3KpqR9lIFLxNfk1V6mo9RFK1cdsZBhloM9kkhOOyGCFuM3otlPtYyzLwCOjNaeWYIEhCgNnhCBpcYMAp2e7kBzpiwGhQmgiQyN8su8nuaJrGCEH5FnW83VQ"}], "types": ["park", "point_of_interest", "establishment"], "reference": "CmRRAAAAojLZnGUVM-9JZuBDDuHICjl4eKAPPcHmEN_x0nOTVqqs7b7M6qe6mMBO218jGcZze_HEfj9EbrDjJ4vqjlwmNGJuoDPRkcBRAXbhgyM2Kps0k-HkKfVk-bei1C_SSW5uEhD-HTvkWf4nzGWuP3Ta8-BUGhTZZ2L56MW4k2Dnr7vpt1l7VqyYrA", "name": "Peckerwood Garden Conservation Foundation", "rating": "NA", "id": "e618a4c618cd67ce4f5fdc165f640220ab3b53b2", "job_title": "Ranger-6b982a83", "place_id": "ChIJmUR7pvHKRoYRIIl0o73bPGE", "address": "20559 Fm 359 Rd, Pine Island, TX 77445, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.64386449999999, 29.7515036], "type": "Point"}, "properties": {"photos": [], "types": ["point_of_interest", "establishment"], "reference": "CmRRAAAAgww28zyakDaO15ClBEKgrW4BYSMTDnGzV-rYN8gZmL7fe4FbrHmDRl5E9YXjx_0df2nUkHurGtC9Xcj3PD8_VUe6kZSlhXzm7uq4H3gchU7AEQ1u9nzgfxzCLpgAWfC0EhCkejSFpmRQXWJCgfbEik2LGhQCgpEIawymNJ6L-S4lhbSdYecZDg", "name": "H2O Conservation Technology", "rating": "NA", "id": "30c07988ef8dfc62dac712b9d587daa4a36f2539", "job_title": "Ranger-6b982a83", "place_id": "ChIJIWZRKeHKQIYRXxta3wOMGGc", "address": "1725 Hwy 6, Houston, TX 77077, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.5705632, 29.7714443], "type": "Point"}, "properties": {"photos": [{"width": 3024, "height": 4032, "html_attributions": ["<a href=\"https://maps.google.com/maps/contrib/108143329814504597326/photos\">State from Jake farm</a>"], "photo_reference": "CoQBdwAAAC8SOuyy1pncwSwBFrpnk8GVqu3sbEcARQqg_IXUEJzMoq_H6UKmxWaOnoxP8JQtHXChrP1GiEsaku91UMZrHSeOL9sXqnKKTjTsZevpYrcuzP216Xns9Xiu_KosAx4x0H47asvjO0PFAorZXMPfxU1fo0BmzZOjW20DWLQZnKg1EhC584w4Rf6_O0VGNsRuJW0GGhTcGMFz_Am8JqdzEb221zMnvodFCw"}], "types": ["park", "point_of_interest", "establishment"], "reference": "CmRSAAAA1GTgMHSTjRT80e5USuo9aqEv13-RcBSBBGa3BN4ubPlu2yyUJ0ySrg1nZhN2jth7YEPLrogFiFc1wJQWNPqz-mmStueg4_spHcu9qRZFmMZrTO3zz4Wi24kiu96T_BkBEhDaV9HkSAK3PAyeLXVybHd2GhSQlo-johgmjqHh4JIJvsD0kvL_jA", "name": "Houston Audubon Society", "rating": 5, "id": "050a5458d86bdd1cee7b09678bd6256d0a20a73e", "job_title": "Ranger-6b982a83", "place_id": "ChIJlQOxwVDbQIYR2uX_TZl0TYc", "address": "440 Wilchester Blvd, Houston, TX 77079, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.56820189999999, 29.770778], "type": "Point"}, "properties": {"photos": [{"width": 1800, "height": 1200, "html_attributions": ["<a href=\"https://maps.google.com/maps/contrib/108765250995932379967/photos\">Audubon Docent Guild</a>"], "photo_reference": "CoQBdwAAANpJv8ECFctnnNGXeqanha_1HHwWR6X4xTQ3AUmxgFCJRrS9B5VbBp4OC8s6P3BkhecNZG8VncxeNn_E_GvNP-vTF52pJdIvy9oWY9DFzBiPynrixBxVvj89uT8oE3i2EdPu5D2Kyx0e9HBNbqWFohHioOLANiHe1VilAKA9z7vFEhBTCcqLcWSN_ARELuCQHUMUGhS_7V3JigSSVkwxnyqPMUPhM_vpVQ"}], "types": ["park", "point_of_interest", "establishment"], "reference": "CmRSAAAAF7akKJf-ztxmzjTBDno6SyW6LjMzOzwboso1QltThDSvMCZOoQTMi1cQeeHLdh88CbLnPb7CkFOMD21pLmFvEvw1XWFQct9On1qiRgZNsv7IffQqRFeDXx1rpdEJBnX2EhBcYscu_bBSKLwnPKXHtRJaGhSoqwf6uHnFhBNN8TY0GdN8_D9vMQ", "name": "Audubon Docent Guild", "rating": 5, "id": "7ddd5daf76cc4979e2ba6b062322d1c77d5d1c07", "job_title": "Ranger-6b982a83", "place_id": "ChIJI9XyNFHbQIYRtwHb8EtTpeU", "address": "440 Wilchester Blvd, Houston, TX 77079, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.42932479999999, 29.7259696], "type": "Point"}, "properties": {"photos": [], "types": ["point_of_interest", "establishment"], "reference": "CmRSAAAABebNnS5D0D5cfqdNOp0Lw-zJ2dIFuzLowLVtMkgmDrUtwJv7EqLPz073K0sN2uLUnQ4_aPZ9Z5j-4va06LKQJIgjVp5BqNGllRegUZAkZ1vBKoQBSJgYwSIKvEck0VlwEhAxNzQHgMdkUVNZi2uZbRGAGhTBZCiBK7pAUPm4lTRuT3qAXqPMXQ", "name": "ABC 13 KTRK-TV", "rating": 4.4, "id": "fa481cef09023e2007970bc05c7c834e3753f74e", "job_title": "Aws-Truepower", "place_id": "ChIJPwXfeQzBQIYRPxpShrzYFMM", "address": "3310 Bissonnet St, Houston, TX 77005, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.3877076, 29.76037609999999], "type": "Point"}, "properties": {"photos": [{"width": 2448, "height": 3264, "html_attributions": ["<a href=\"https://maps.google.com/maps/contrib/117578048426466338573/photos\">Ankeel Bhakta</a>"], "photo_reference": "CoQBdwAAAPZEDi3DNWFgWj6VJ1SzzBMat2o2unK2bSJ45auaGCV0Y9Ts0Fqy9XvJDHw-cVBgaZMslmGBpj3kAsYIQkaTON8aJhosFhe7-aFyT_lfwFxJlMsaoFM31eHcwR8Ohl01doZzicdbGlXuxDEQIe1kN_PHX_5Jote0oJ-6ymPVYKqlEhAEGYzFdrcO1XO0DzUf4iqNGhQthpIXMWm8V2BJpU_y5Zbqy1NCSA"}], "types": ["point_of_interest", "establishment"], "reference": "CmRRAAAAw9cne3ZuwR4qElck3e5Dc8YMK3C2dls56YmSM_8uoYg24iZZKdwpYnwLB3mzSrfEoI0vUXnws5okOabKY54PmHHxRfPINVjrePU1eRecDD-ncF_r8W7Eek38xsmM9MAlEhAaurFGqrsV8HzjZC8cmmekGhQoK3cAZi7W3MfQT0IfiIKa7Ay7wQ", "name": "KHOU-TV Channel 11", "rating": 4.3, "id": "477c041b283f64d17cebe0b7da92d10bc3fcb72e", "job_title": "Aws-Truepower", "place_id": "ChIJOddsmlC_QIYR7bYpKYiJmg0", "address": "1945 Allen Pkwy, Houston, TX 77019, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.42932479999999, 29.7259696], "type": "Point"}, "properties": {"photos": [], "types": ["point_of_interest", "establishment"], "reference": "CmRSAAAAGE_LtyFAYxGSm7THi7-tubw42yhh112Br0AUVH9YseROWRnyA31Rzfk64ABO16vRrHxkF2EUpQTAWzRxqE-ydmw6YLY9LdtB_3IckR2UdXFFtVkvEs1g6x05NpBPa525EhAR76w-WmuzUruKbuc9po3UGhSBW0AZi6SVSUpKbiMV7INfTETKpQ", "name": "ABC 13 KTRK-TV", "rating": 4.4, "id": "fa481cef09023e2007970bc05c7c834e3753f74e", "job_title": "Waterman-Broadcasting-1", "place_id": "ChIJPwXfeQzBQIYRPxpShrzYFMM", "address": "3310 Bissonnet St, Houston, TX 77005, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.3877076, 29.76037609999999], "type": "Point"}, "properties": {"photos": [{"width": 2448, "height": 3264, "html_attributions": ["<a href=\"https://maps.google.com/maps/contrib/117578048426466338573/photos\">Ankeel Bhakta</a>"], "photo_reference": "CoQBdwAAAJLqmYuRLOzLNcqTvWIPRiOUYA7QMP7PZHKzOYdTDqoIlE2bWieRouBrJHvXPjtkdWV15dNd7YiZ4ey6woch5Tln_D4SrK2445cnElW-bJ0mVd2Tw0RrzMrXjsjE-DKT5_nsF-dSAsL24VyU_OiSWIHGUxhLMn-Cbj89Ylzx73_JEhBsm3uioq1tA4ygh4Ej2xlaGhTX4u601jdCHYqfW-9Rxy4OqBJ4cw"}], "types": ["point_of_interest", "establishment"], "reference": "CmRRAAAA_AjL3dK7U405vfiXVvU-SNSP7tuMspJ8_hMdyrYwkKIrYROma4U58dZ9ohSgaORzZlaBW5GpQPL7ym7RY4cp-NDl9u7xIURbD95OLWU0qeRemPvn_iQ9HyDVJ-eFKRJfEhDmLg823Dl5lobjbHo2fcpYGhTXXMG2WVNoy51AyI1AfUDAqjZiCw", "name": "KHOU-TV Channel 11", "rating": 4.3, "id": "477c041b283f64d17cebe0b7da92d10bc3fcb72e", "job_title": "Waterman-Broadcasting-1", "place_id": "ChIJOddsmlC_QIYR7bYpKYiJmg0", "address": "1945 Allen Pkwy, Houston, TX 77019, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.42932479999999, 29.7259696], "type": "Point"}, "properties": {"photos": [], "types": ["point_of_interest", "establishment"], "reference": "CmRSAAAAPeQcoAbWLexHFcV_wBf7GRCXCB3Mps2JUk3nZFENyFbLysN9D_WYYnSvz5eSppfoM8hGW1baCmLE6LLUaHAnDUQgx9c2WXhKpKBxpwzunT07eJaiqHWXPzpe2YTyRSQTEhDZxKKelGVZ2OnkcPkLQUpRGhTePDCJqh2OFsxEOptLC3vb3W_puA", "name": "ABC 13 KTRK-TV", "rating": 4.4, "id": "fa481cef09023e2007970bc05c7c834e3753f74e", "job_title": "Weather-Group", "place_id": "ChIJPwXfeQzBQIYRPxpShrzYFMM", "address": "3310 Bissonnet St, Houston, TX 77005, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.3877076, 29.76037609999999], "type": "Point"}, "properties": {"photos": [{"width": 2448, "height": 3264, "html_attributions": ["<a href=\"https://maps.google.com/maps/contrib/117578048426466338573/photos\">Ankeel Bhakta</a>"], "photo_reference": "CoQBdwAAAPbU21v4r8XceqUPfiCWX87WQr3Y_fc2GykdLL748R34SyeDO4TLVFxxppkjgmou9fOCzITwHokE896HIaPUc_SyQYf6gro7Jxz_DaMlwNWM_K8Knu09gCGncRfwQoosvCeCA6xfrvuDooSybOG3AMuANxjiG5VEsBaIoRlWyZhDEhDhVocL7yvUkHeOzjJlIz2UGhT-6O5Thn9j5OdaC99ZAAe1nVbmJQ"}], "types": ["point_of_interest", "establishment"], "reference": "CmRRAAAANbQJQPYQtpqwjcDzt5Q0uq1fQ_4_NFUzP6yuiiM0bHZbtNNFNw7WdwC2gBJD2cYevlp2s8D7pqJ2a-eeYknZXDKtzVyCxJ0aXYz01APYXeaQJN0J_8b7xp6kgJzYg7bNEhD__YCuXTwrSXaH9oP33hWBGhREymNZO-KYHTh934xKbZgYna4b8A", "name": "KHOU-TV Channel 11", "rating": 4.3, "id": "477c041b283f64d17cebe0b7da92d10bc3fcb72e", "job_title": "Weather-Group", "place_id": "ChIJOddsmlC_QIYR7bYpKYiJmg0", "address": "1945 Allen Pkwy, Houston, TX 77019, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.42932479999999, 29.7259696], "type": "Point"}, "properties": {"photos": [], "types": ["point_of_interest", "establishment"], "reference": "CmRSAAAAjKR5YRN8hQ2a69Rn-g4Z8_al0FIyICKswFGbbblhfWCOLUc1P_eXLm6jjBU4C6KGKGkpz5CqRDgXkWJ4QVltXOJgIHBGQIpZt_XIAozFeGFIaadwJ_b8Lks9FOjvTFPdEhBkzJvy5VLvS3sro9CCwFxIGhRg-88qXuAi8Awn3Ae7fUQVhZCjnw", "name": "ABC 13 KTRK-TV", "rating": 4.4, "id": "fa481cef09023e2007970bc05c7c834e3753f74e", "job_title": "Kulr--8-Tv", "place_id": "ChIJPwXfeQzBQIYRPxpShrzYFMM", "address": "3310 Bissonnet St, Houston, TX 77005, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.3877076, 29.76037609999999], "type": "Point"}, "properties": {"photos": [{"width": 2448, "height": 3264, "html_attributions": ["<a href=\"https://maps.google.com/maps/contrib/117578048426466338573/photos\">Ankeel Bhakta</a>"], "photo_reference": "CoQBdwAAAH70_66M5wDNeJiCRwRU-1OFMi32oLGTd4d0wz3J_8Pye4tkECX74R16xhU4UorGvKcHoKDKF_U60KyNHexCZ2H8iibHU2mKBZ6r_4YqGRD1K7_2Od7_HjGy3JuYsqaheBFqeaGBxyHt4Vxd17kS9gsm_n5Cqn_KEv5XNKs8g-TBEhBWVceYfspKnpKXCavGwy7kGhSjd8QTJEHbDURLeGIbMBE9t8IVVA"}], "types": ["point_of_interest", "establishment"], "reference": "CmRRAAAAqailF2Ro9reGbzv8tZnmgfg5YZCSTCeWN5vPG2YDVoViAD8QEDegX3MGRWbJDhOY2Mmi5-d4qg-bY5cBtx-nFpygzLOx4sYgvdBcL0wrz7_0DrCMihcHWEoI7dRl6HNsEhBhiEgdf4MfVVSl49CHta-EGhREw6vlsf1U-20moIehSL0JaMOmFw", "name": "KHOU-TV Channel 11", "rating": 4.3, "id": "477c041b283f64d17cebe0b7da92d10bc3fcb72e", "job_title": "Kulr--8-Tv", "place_id": "ChIJOddsmlC_QIYR7bYpKYiJmg0", "address": "1945 Allen Pkwy, Houston, TX 77019, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.42932479999999, 29.7259696], "type": "Point"}, "properties": {"photos": [], "types": ["point_of_interest", "establishment"], "reference": "CmRSAAAAlpo5w_ZozinfxSVn8zFIAarWiX7cqmMBGwHREVMKEsjLv8grBmihLYgwDQc-Wc5QmtTQywgE4_-sxRCPxDIlEnwfBnDP_S1OMmJX0fCjZi0NNjzUC2fopIIE6azWJwcWEhBEHhywxP74unjP4hi6giOMGhQotRs_oy-q8CW0sOvBxdY0Sqhb9g", "name": "ABC 13 KTRK-TV", "rating": 4.4, "id": "fa481cef09023e2007970bc05c7c834e3753f74e", "job_title": "Engility-Corp", "place_id": "ChIJPwXfeQzBQIYRPxpShrzYFMM", "address": "3310 Bissonnet St, Houston, TX 77005, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.3877076, 29.76037609999999], "type": "Point"}, "properties": {"photos": [{"width": 2448, "height": 3264, "html_attributions": ["<a href=\"https://maps.google.com/maps/contrib/117578048426466338573/photos\">Ankeel Bhakta</a>"], "photo_reference": "CoQBdwAAAIKN-o5tgvGI3BrBLg85DNmo2YBYU494PpK_X6Sl2CqgeCxwqj_PhRGmNFHmmgZ-RmTE6VHxBIZMS-yulal1tPo5AzM2qw0x-1B0CC3Pv1BRemY07eKvjDE4VtuCCilaLy_DwkRBUgtGUnwbdykpjAPEcro-OI3YZgDxcafFDwhaEhBJNX4aG_EOE9xDaWkKCOEKGhTWMKyGKsbJd-lwfxqE0EFEXmPbgw"}], "types": ["point_of_interest", "establishment"], "reference": "CmRRAAAAzYEI7LLtrEhMiNCT5LIYcry_0yxn2MWbPUy_9QmakRRhYHU-aqe5s3aG3p8IhHfluJ7CwbrHNh4abOpXINdO6J5A5P5p764YN914AyFe_2x_eHkrEa0oFC1mHnIaRZ3cEhB_eCGok_EZRI_BntgN9JLlGhT8KT-oI9halt-TeqjiLxY90EI6pw", "name": "KHOU-TV Channel 11", "rating": 4.3, "id": "477c041b283f64d17cebe0b7da92d10bc3fcb72e", "job_title": "Engility-Corp", "place_id": "ChIJOddsmlC_QIYR7bYpKYiJmg0", "address": "1945 Allen Pkwy, Houston, TX 77019, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.42932479999999, 29.7259696], "type": "Point"}, "properties": {"photos": [], "types": ["point_of_interest", "establishment"], "reference": "CmRSAAAAArlx8ZSg29g0h9w3M8eDYrzUZGqD-5z3ipJZ5jdf4c1Fee-N7KIpXpYPZiiJNzupg_SaVtFZ-Re6OnKGSbdeRlMds-flcDu4h4kGmC9aqg1stLNUdNt6UC2h375Xo70OEhAUbfn5sS6a1xRYhN8qJmwfGhQQTyAsbjILzxUAhc8PodAfzDorEw", "name": "ABC 13 KTRK-TV", "rating": 4.4, "id": "fa481cef09023e2007970bc05c7c834e3753f74e", "job_title": "Centuria-Corporation", "place_id": "ChIJPwXfeQzBQIYRPxpShrzYFMM", "address": "3310 Bissonnet St, Houston, TX 77005, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.3877076, 29.76037609999999], "type": "Point"}, "properties": {"photos": [{"width": 2448, "height": 3264, "html_attributions": ["<a href=\"https://maps.google.com/maps/contrib/117578048426466338573/photos\">Ankeel Bhakta</a>"], "photo_reference": "CoQBdwAAALb7386GssMW0XiUP8LM2tdlyg0qTks9pE3aWaZqhCTjsl7E4TQ7FRKwY5M4vTCbiSL-wh6usfQpFMjcNEdt_cqA13MjOUVTD0bNeBjmy42L6UrNcV7nkw_kLzNVwE9YucJRs69J06uQ5S-MuOOwBvKJd57b6K7ahO5LpxY0VoY5EhA3sMR2I-vayGty7WLcDvW6GhToVDkM1C1DFV8Esa2f3Rk5De6jlg"}], "types": ["point_of_interest", "establishment"], "reference": "CmRRAAAAxXgK_VYqZqoJqM3fdwTEpAfM6Cml4_BRRJYbaCF9ZqU7iwB4LmkgRtuwpVGDFTSmfJa5DJKIuci8aOsC3oZkQ-pFZ3UYFOYEmLOX0aGX0qbXMvWf9EVV-zSicOrQ4QpeEhAy5nQeX3L92oZeZLl-k_nIGhRWMGBWh6pwCf4tBHMxP9gC9DXeIA", "name": "KHOU-TV Channel 11", "rating": 4.3, "id": "477c041b283f64d17cebe0b7da92d10bc3fcb72e", "job_title": "Centuria-Corporation", "place_id": "ChIJOddsmlC_QIYR7bYpKYiJmg0", "address": "1945 Allen Pkwy, Houston, TX 77019, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.42932479999999, 29.7259696], "type": "Point"}, "properties": {"photos": [], "types": ["point_of_interest", "establishment"], "reference": "CmRSAAAA6NZDA65CBKToBNUCHqopzMeipxrtiEwj_DiHDZy0GJGEbxzDYo7nlPebLRHN-Y-LkWPb4e56-qv1M70SV1buMwBB7iLzslimMPwGOq5mUtPjFIzxuaXIReN86JiZ5eswEhDgkXjJORoWfAVN3O2Rk5UYGhRfFxNCGlitrysriDv3hLCtGkT4mA", "name": "ABC 13 KTRK-TV", "rating": 4.4, "id": "fa481cef09023e2007970bc05c7c834e3753f74e", "job_title": "Tribune-Media-Company", "place_id": "ChIJPwXfeQzBQIYRPxpShrzYFMM", "address": "3310 Bissonnet St, Houston, TX 77005, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.3877076, 29.76037609999999], "type": "Point"}, "properties": {"photos": [{"width": 2448, "height": 3264, "html_attributions": ["<a href=\"https://maps.google.com/maps/contrib/117578048426466338573/photos\">Ankeel Bhakta</a>"], "photo_reference": "CoQBdwAAAIsng0ywzOISw2LBk9yBC-HOl23HnEDgGeQCDH6fA8Zz25yZ84MOLb_NIo9ZL-anjK0xXrkUJsTJ98klThIMREiLX6fmSWSlZu5r39sJcmX7EgWA78wUgVS_YPVk-NAE9CIh5jy0s61wRgi8Fx6icLollYLKK8fSVT5dalUepBg9EhDlNOKy10D5QfUXxCwFKk5iGhSYW64JcQHgpzhYMvEjDjGigS_PrQ"}], "types": ["point_of_interest", "establishment"], "reference": "CmRRAAAAIwv3rEsNhmkaIS_IoKkDwaVO2PEpv4MnAnvXptJaguIAFslGt0ERC1StzxyvZPw25a7oNr8CZE_C3Yq8Yn2dsAczyEF8G6fC-vdFj7O-LSz1SP_qiab0Lq4TjGEEtqj6EhBv30vPZO81xbV_tUBu--GwGhSw0CEBSg_6tqfBN0xBkk3NGkpLNw", "name": "KHOU-TV Channel 11", "rating": 4.3, "id": "477c041b283f64d17cebe0b7da92d10bc3fcb72e", "job_title": "Tribune-Media-Company", "place_id": "ChIJOddsmlC_QIYR7bYpKYiJmg0", "address": "1945 Allen Pkwy, Houston, TX 77019, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.42932479999999, 29.7259696], "type": "Point"}, "properties": {"photos": [], "types": ["point_of_interest", "establishment"], "reference": "CmRSAAAAjKR5YRN8hQ2a69Rn-g4Z8_al0FIyICKswFGbbblhfWCOLUc1P_eXLm6jjBU4C6KGKGkpz5CqRDgXkWJ4QVltXOJgIHBGQIpZt_XIAozFeGFIaadwJ_b8Lks9FOjvTFPdEhBkzJvy5VLvS3sro9CCwFxIGhRg-88qXuAi8Awn3Ae7fUQVhZCjnw", "name": "ABC 13 KTRK-TV", "rating": 4.4, "id": "fa481cef09023e2007970bc05c7c834e3753f74e", "job_title": "Weathervision-Wxvo--tv", "place_id": "ChIJPwXfeQzBQIYRPxpShrzYFMM", "address": "3310 Bissonnet St, Houston, TX 77005, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.3877076, 29.76037609999999], "type": "Point"}, "properties": {"photos": [{"width": 2448, "height": 3264, "html_attributions": ["<a href=\"https://maps.google.com/maps/contrib/117578048426466338573/photos\">Ankeel Bhakta</a>"], "photo_reference": "CoQBdwAAAH70_66M5wDNeJiCRwRU-1OFMi32oLGTd4d0wz3J_8Pye4tkECX74R16xhU4UorGvKcHoKDKF_U60KyNHexCZ2H8iibHU2mKBZ6r_4YqGRD1K7_2Od7_HjGy3JuYsqaheBFqeaGBxyHt4Vxd17kS9gsm_n5Cqn_KEv5XNKs8g-TBEhBWVceYfspKnpKXCavGwy7kGhSjd8QTJEHbDURLeGIbMBE9t8IVVA"}], "types": ["point_of_interest", "establishment"], "reference": "CmRRAAAAqailF2Ro9reGbzv8tZnmgfg5YZCSTCeWN5vPG2YDVoViAD8QEDegX3MGRWbJDhOY2Mmi5-d4qg-bY5cBtx-nFpygzLOx4sYgvdBcL0wrz7_0DrCMihcHWEoI7dRl6HNsEhBhiEgdf4MfVVSl49CHta-EGhREw6vlsf1U-20moIehSL0JaMOmFw", "name": "KHOU-TV Channel 11", "rating": 4.3, "id": "477c041b283f64d17cebe0b7da92d10bc3fcb72e", "job_title": "Weathervision-Wxvo--tv", "place_id": "ChIJOddsmlC_QIYR7bYpKYiJmg0", "address": "1945 Allen Pkwy, Houston, TX 77019, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.42932479999999, 29.7259696], "type": "Point"}, "properties": {"photos": [], "types": ["point_of_interest", "establishment"], "reference": "CmRSAAAANPenbyeqcesAQnjxO8imm-DHzPkDfA6_v6b6KHKud81-fqlDn9MU5bGnnjoBpsc654zoQIMLSX8Qym6QLtUhU_ydb338tznpA31CjKgkQBESmc_JLcexqHRA_yjCNGD9EhB1XfqFEOebeiR7D9n7S5HsGhQKn910nhhqqCOLpkVgwrtuhQzYpg", "name": "ABC 13 KTRK-TV", "rating": 4.4, "id": "fa481cef09023e2007970bc05c7c834e3753f74e", "job_title": "Nexstar-Broadcasting", "place_id": "ChIJPwXfeQzBQIYRPxpShrzYFMM", "address": "3310 Bissonnet St, Houston, TX 77005, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.3877076, 29.76037609999999], "type": "Point"}, "properties": {"photos": [{"width": 2448, "height": 3264, "html_attributions": ["<a href=\"https://maps.google.com/maps/contrib/117578048426466338573/photos\">Ankeel Bhakta</a>"], "photo_reference": "CoQBdwAAANSwsXKQ6A_wjeCkXcg8Wvi0NyTSCSXyWMXYjEeEFvri7idoLCYbCfY1RTejksOcuwVsaDv9rd2QTEfBlHe-ray-RwoeP3uYuWRnmWLwApk7W50L3CvRdxE8yZa79akE-Q7U8FDICRruIn_doCF3dTAaXElbkKKdN4oAJsqbL1RFEhDCQt9Lq4ergkDYRlhmI3GWGhQ2BFH5NYYrNUXArTBVQFwbPAi_iQ"}], "types": ["point_of_interest", "establishment"], "reference": "CmRRAAAAEDmK0YPBwO7BRQdvoQplO7c37VdCCxRpy0FkMX9XG7WaCfY96r8T8dcN6lrY-lfXEKBuBmAD_zDFYNe-Voh4Mp1FilMr9FBT9Bv12S5fBvJP-qiGyjI5RnhwTpDYPkAIEhACtD3OD5PQEIn2IRy6dErRGhRwQmbgp5mdI9TxFJdZW_q9_xh7Ew", "name": "KHOU-TV Channel 11", "rating": 4.3, "id": "477c041b283f64d17cebe0b7da92d10bc3fcb72e", "job_title": "Nexstar-Broadcasting", "place_id": "ChIJOddsmlC_QIYR7bYpKYiJmg0", "address": "1945 Allen Pkwy, Houston, TX 77019, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.42932479999999, 29.7259696], "type": "Point"}, "properties": {"photos": [], "types": ["point_of_interest", "establishment"], "reference": "CmRSAAAAYOvZkl5aVVEPac0tM5GFlouicZt6kR1wOQCqoJJdnIHYDYe0E4snmYF2hYTMCNujDBRwNOfZwY98GWjnd-8wMesHc2VH8N7pFKoqytFWxPvf6U-YGZkjGJ51SyZWt5SyEhBq587T5giCrl_EFNKWDtY7GhTP7f29aKROiSukIU_KixEZrPRBBQ", "name": "ABC 13 KTRK-TV", "rating": 4.4, "id": "fa481cef09023e2007970bc05c7c834e3753f74e", "job_title": "Bloomsky-Inc", "place_id": "ChIJPwXfeQzBQIYRPxpShrzYFMM", "address": "3310 Bissonnet St, Houston, TX 77005, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.3877076, 29.76037609999999], "type": "Point"}, "properties": {"photos": [{"width": 2448, "height": 3264, "html_attributions": ["<a href=\"https://maps.google.com/maps/contrib/117578048426466338573/photos\">Ankeel Bhakta</a>"], "photo_reference": "CoQBdwAAABjdY_Nya6-nQs2mDMnaeSP7T3YwNkxkypKn708fZ9rsyUswStTylB8BD16nnGptXXJnmrVWIEnNCUI5StyIOX8TZhRq5J98nsjxDOAI9PR-2Z-PC66URqXQwFE1m5FV4v_AkRKsIEIrdtUvKfcM1iawtQTKysH1LwRELSIxHAooEhC9UT9ttzn-g8QiyVx0tSQUGhRm_s-hj5TU4xyn4UgeKq-HADAFpQ"}], "types": ["point_of_interest", "establishment"], "reference": "CmRRAAAAU6I1aDjaN0eZkU1fZww3_vgKG2X55ZNgL9904Hax3H_NPWSg_zhEmSNfYLOt7hZjU74Egwi3b8h-6vbZ0-A-B8E7OTwcqzlGhEDpEx95KRUbhAUiZpOFSj4sLMAuunnUEhDU0mDODfqPbeAXCY7M3PyXGhQEazwUFalK70-2yYq7SeQEDG-V9Q", "name": "KHOU-TV Channel 11", "rating": 4.3, "id": "477c041b283f64d17cebe0b7da92d10bc3fcb72e", "job_title": "Bloomsky-Inc", "place_id": "ChIJOddsmlC_QIYR7bYpKYiJmg0", "address": "1945 Allen Pkwy, Houston, TX 77019, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.42932479999999, 29.7259696], "type": "Point"}, "properties": {"photos": [], "types": ["point_of_interest", "establishment"], "reference": "CmRSAAAAD-GVw3SU4rCt1G-5dYI4RnmnCwCgFTOKzET-rvUVZ9ZVAkVozl3Npk5sLNlOqElw3iPxyn9pQhJ_3wxMn0ie7ulkmcbYow0kXfKy_nIDHDiQxVKF5nGfaRIx7eB_xXJlEhBdEfDvpUnCKeNutSHsWJ83GhSv-xDc0yfoE2JC8BkfHgUXsXAuig", "name": "ABC 13 KTRK-TV", "rating": 4.4, "id": "fa481cef09023e2007970bc05c7c834e3753f74e", "job_title": "Cox-Media-Group", "place_id": "ChIJPwXfeQzBQIYRPxpShrzYFMM", "address": "3310 Bissonnet St, Houston, TX 77005, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.3877076, 29.76037609999999], "type": "Point"}, "properties": {"photos": [{"width": 2448, "height": 3264, "html_attributions": ["<a href=\"https://maps.google.com/maps/contrib/117578048426466338573/photos\">Ankeel Bhakta</a>"], "photo_reference": "CoQBdwAAANTmP09oOn6EQqAPJDxNj-YfUKQ5QEu-QE4TDA1ntEWYFLkrvHmxs1gYEdpaIvKPVbAbtRuUc-RZ0fAKlv9SOTI3igeOTZzS8R2xQwskVmsbmrB59GJZFaV8PSRC3abgSA-NPJlXxh9L-MVpgOf44NP7-L3tfWLX4oyXqi0g_ROuEhD9l8l9-huTmvhuSzRNParaGhTsAjsw81YrS-gWxqQKVeLBvhO9Aw"}], "types": ["point_of_interest", "establishment"], "reference": "CmRRAAAAK3yvnkMbA6Q_VwebKr6KyXnX225fkN2IMlW3AqiOD2QTDRrDQ4SsTiKDesDfw-c-ifbMz3IXS-Qw9kaF6jC6KeF87jsycs4VdBWSZcoRbP27kDUZ76In5Q_Fi1eA1FjdEhB-7X6XSP_wq_XBTUZYx_DpGhRXtA1w0IdvRorwpBhg8nlm8ut8xw", "name": "KHOU-TV Channel 11", "rating": 4.3, "id": "477c041b283f64d17cebe0b7da92d10bc3fcb72e", "job_title": "Cox-Media-Group", "place_id": "ChIJOddsmlC_QIYR7bYpKYiJmg0", "address": "1945 Allen Pkwy, Houston, TX 77019, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.42932479999999, 29.7259696], "type": "Point"}, "properties": {"photos": [], "types": ["point_of_interest", "establishment"], "reference": "CmRSAAAAT2xFm81DjcDQV8cAMLa1obCz0_VIs8fDGNXiMbrDhgDCDX7WBZbQ2RF4V0W7cYEaPPS_b4nhu0O6tufpmVCjLDUnGP56oZPaDiGpq_mt4g5fOecsdl2TiJ4fPaZ0UWltEhA_GWLnsB3KdWRvBUPeyyzAGhT2Ea7f83-rdyei6nFpmmC309pYug", "name": "ABC 13 KTRK-TV", "rating": 4.4, "id": "fa481cef09023e2007970bc05c7c834e3753f74e", "job_title": "Heritage-Broadcasting", "place_id": "ChIJPwXfeQzBQIYRPxpShrzYFMM", "address": "3310 Bissonnet St, Houston, TX 77005, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.3877076, 29.76037609999999], "type": "Point"}, "properties": {"photos": [{"width": 2448, "height": 3264, "html_attributions": ["<a href=\"https://maps.google.com/maps/contrib/117578048426466338573/photos\">Ankeel Bhakta</a>"], "photo_reference": "CoQBdwAAAGF9b28I_dGwRoiHqtVuOjC-6UZbB0QjTISzfkYbeqe0BmWWBjxzhyzdBs23TDAAgondu4GobFMpMSGdHY7gIDxW9r-qmY3K3jMdTSa7KmCUjR4QrCdhBggTOrMvhuzMMhvWYuCJCUAk5fq7kW5J2OIJm7enT-WL-UlPs4yyem2tEhBtL1XkwNlRE9EYZs6LA1ueGhTru03b1ltSe0TVV43kniIaBXmJBg"}], "types": ["point_of_interest", "establishment"], "reference": "CmRRAAAA1euceKT6ezEqBQ-hQRLQLoBjnN53ltsBeJo52xz2GCQ1XER-Vwh7B0ATcMAomj_wIpLqoR1Tie4YcMx6slDPVzq0MVFO4fStI8f4Zd3oqQV_4UOA6btJIWadomjGRQYKEhD51QUHYpsr7hbZTcqWTSL9GhSnHWydQJDyAZmMSC2DcTxvQUQBSg", "name": "KHOU-TV Channel 11", "rating": 4.3, "id": "477c041b283f64d17cebe0b7da92d10bc3fcb72e", "job_title": "Heritage-Broadcasting", "place_id": "ChIJOddsmlC_QIYR7bYpKYiJmg0", "address": "1945 Allen Pkwy, Houston, TX 77019, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.42932479999999, 29.7259696], "type": "Point"}, "properties": {"photos": [], "types": ["point_of_interest", "establishment"], "reference": "CmRSAAAAUZoalbWpa_I08kmKYBABGomTY1aNAbQUBeQDrvN23Vz73SYwIB3ZlLVpb74jPeblUlQh0jfhs2dU336flZZ-mD2PTT-KNSRJOOnVk1ILpEYqIRbPz_2JSH-aZQHleolAEhB7VdhAFgQtaRNZKVpzYZsqGhRxqfekropc_ni4oyl-lED3m_msqw", "name": "ABC 13 KTRK-TV", "rating": 4.4, "id": "fa481cef09023e2007970bc05c7c834e3753f74e", "job_title": "Disney-ABC", "place_id": "ChIJPwXfeQzBQIYRPxpShrzYFMM", "address": "3310 Bissonnet St, Houston, TX 77005, United States"}, "type": "Feature"}, {"geometry": {"coordinates": [-95.3877076, 29.76037609999999], "type": "Point"}, "properties": {"photos": [{"width": 2448, "height": 3264, "html_attributions": ["<a href=\"https://maps.google.com/maps/contrib/117578048426466338573/photos\">Ankeel Bhakta</a>"], "photo_reference": "CoQBdwAAAHFwW4WQTsLd1l2edy6Q7O-gtiMNb2iX1KYRH__PRF1LUak96Qebw-jQhGz6XACIdqREI11QH44I5pOSB5rwabJqhQ7nm-GuZQx-83wwfD0L77SjucCNU9fka8t3aC9iUJJ1ZvKT4FBZDU3pfXOlnpFNmJb9XBMg3EjpyBtFcLs3EhDYJaoDXUK1OmptfuFuQ1UoGhQIxFdq3zGrMQ-hi4MhfaL923RNEA"}], "types": ["point_of_interest", "establishment"], "reference": "CmRRAAAAW4-3rWaN3ZYHNBakoon9bIf9Q4N4tQ2xxkhgPRKSmP5ubfETBLkHJfIPyqlAOWI5aGUi-HRUEYP1dbh6ZWHktnlIxCT_0W0mCheIEVtKYE7ihJH_L_HshyZX8BT4L0tGEhCBDk4Algx0QxVIZXN7swyVGhQZzxJGuIZo0tXEPkFbBBvvloI-fQ", "name": "KHOU-TV Channel 11", "rating": 4.3, "id": "477c041b283f64d17cebe0b7da92d10bc3fcb72e", "job_title": "Disney-ABC", "place_id": "ChIJOddsmlC_QIYR7bYpKYiJmg0", "address": "1945 Allen Pkwy, Houston, TX 77019, United States"}, "type": "Feature"}]

In [68]:
test_asdfasdf

[{'geometry': {'coordinates': [-95.57188149999999, 29.9951915],
   'type': 'Point'},
  'properties': {'address': '126 Vintage Park Blvd N, Houston, TX 77070, United States',
   'id': '979d392b613c49fbb954ee393bff65bda5042b34',
   'job_title': 'Texas-Children%27s-Hospital',
   'name': 'Chemistry',
   'photos': [{'height': 3190,
     'html_attributions': ['<a href="https://maps.google.com/maps/contrib/101403699241874436061/photos">Chemistry</a>'],
     'photo_reference': 'CoQBdwAAABqE-T9AB_70H655NJEo-6sBHiarzn_lCDTymGEOBYaQ_VCbs5x8DzItIaMFqpvhFvBUbKLnyMCbdmHoRSB8Gw9SBv-xixYqs_PO1MkakCQc5G4EUbL2I_OZhF1j1OMRPWWLbJ5LcaqG2gVCFBarTCL5nJlI3x9IBZuWr1GRdY63EhAhLTvv60bmRdTetY-GA-5bGhTqi4LVVI_9NX9ukVkXZFthqRiI7g',
     'width': 4785}],
   'place_id': 'ChIJWxsq_4fSQIYRU9dRPmk8uIw',
   'rating': 5,
   'reference': 'CmRSAAAA7c31MuvbVcIUj2yMiz3WauDMTcw7XdnZdlkrogYIlj0S6fqboTlV5cQpKrKyUielNqkPulDnLu7EAFsz6K1TBgaOdWI1qldreDqAywxQQY3lN9t_vThzZalbCwy1h1GYEhAaQ6uH_SB5CCv7izzBn12_GhTxqvH_YhNeFsTfq1YRorcaE4v

In [69]:
len(test_asdfasdf)

1522

In [ ]:
for each in test_asdfasdf:
    each[]

In [306]:
answer2  = getJSON_from_jobsList_everything(array_of_job_Titles=funcArg["ListJobTitles"],funcArg["pCSV"],funcArg["pGeoJSON"],geographic_limits =funcArg["geo_lim"])

SyntaxError: positional argument follows keyword argument (<ipython-input-306-311feeca933c>, line 1)

In [289]:
test_short_job_title_list

['Chemist',
 'Conservation',
 'Herpetologist',
 'Laboratory',
 'meteorologist ',
 'Naturalist']

In [255]:
#featCollection
list_of_features

NameError: name 'list_of_features' is not defined

## previous error with full list with spaces in job titles:
_title': 'Research and Development Technician'}, {'company': 'Chapin-Hall-At-the-University-of-Chicago', 'job_title': 'Research and Development Technician'}]
each=  Research and Innovation
soup.find(id = 'searchCount') =  <div id="searchCount">Jobs 1 to 10 of 382,916</div>
soup.find(id = 'searchCount') =  <class 'bs4.element.Tag'>
---------------------------------------------------------------------------
gaierror                                  Traceback (most recent call last)
/Users/justingosses/anaconda/lib/python3.5/urllib/request.py in do_open(self, http_class, req, **http_conn_args)
   1253             try:
-> 1254                 h.request(req.get_method(), req.selector, req.data, headers)
   1255             except OSError as err: # timeout error

/Users/justingosses/anaconda/lib/python3.5/http/client.py in request(self, method, url, body, headers)
   1105         """Send a complete request to the server."""
-> 1106         self._send_request(method, url, body, headers)
   1107 

/Users/justingosses/anaconda/lib/python3.5/http/client.py in _send_request(self, method, url, body, headers)
   1150             body = _encode(body, 'body')
-> 1151         self.endheaders(body)
   1152 

/Users/justingosses/anaconda/lib/python3.5/http/client.py in endheaders(self, message_body)
   1101             raise CannotSendHeader()
-> 1102         self._send_output(message_body)
   1103 

/Users/justingosses/anaconda/lib/python3.5/http/client.py in _send_output(self, message_body)
    933 
--> 934         self.send(msg)
    935         if message_body is not None:

/Users/justingosses/anaconda/lib/python3.5/http/client.py in send(self, data)
    876             if self.auto_open:
--> 877                 self.connect()
    878             else:

/Users/justingosses/anaconda/lib/python3.5/http/client.py in connect(self)
   1251 
-> 1252             super().connect()
   1253 

/Users/justingosses/anaconda/lib/python3.5/http/client.py in connect(self)
    848         self.sock = self._create_connection(
--> 849             (self.host,self.port), self.timeout, self.source_address)
    850         self.sock.setsockopt(socket.IPPROTO_TCP, socket.TCP_NODELAY, 1)

/Users/justingosses/anaconda/lib/python3.5/socket.py in create_connection(address, timeout, source_address)
    692     err = None
--> 693     for res in getaddrinfo(host, port, 0, SOCK_STREAM):
    694         af, socktype, proto, canonname, sa = res

/Users/justingosses/anaconda/lib/python3.5/socket.py in getaddrinfo(host, port, family, type, proto, flags)
    731     addrlist = []
--> 732     for res in _socket.getaddrinfo(host, port, family, type, proto, flags):
    733         af, socktype, proto, canonname, sa = res

gaierror: [Errno 8] nodename nor servname provided, or not known

During handling of the above exception, another exception occurred:

URLError                                  Traceback (most recent call last)
<ipython-input-215-31fbce623b6f> in <module>()
----> 1 getJSON_from_jobsList_everything(array_of_jobTitles=funcArg["ListJobTitles"],FilePath=funcArg["pCSV"],path=funcArg["pGeoJSON"],geographic_limits =funcArg["geo_lim"])

<ipython-input-213-69bd9f374f10> in getJSON_from_jobsList_everything(array_of_jobTitles, FilePath, path, geographic_limits)
      1 def getJSON_from_jobsList_everything(array_of_jobTitles,FilePath = "../DATA/placeholder,csv",path="../DATA/placeholder.geojson",geographic_limits = geographic_limits):
----> 2     list_of_CompaniesAndJobs = runMultiple_skills_info(array_of_jobTitles)
      3     saveArray_of_JobSearchResults(arrayOfJobsAndSearchTerm = list_of_CompaniesAndJobs, FilePath = "../DATA/placeholder.csv")
      4     make_geojson_from_CompanyJobList(company_list_formatted = company_array_formatted,path="../DATA/placeholder.geojson",geographic_limits = geographic_limits)
      5 

<ipython-input-43-99f3c0054790> in runMultiple_skills_info(array_of_jobTitles)
      4         print('each= ',each)
      5         #temp_results1 = []
----> 6         temp_results1 = skills_info("Houston","TX",each)
      7         if temp_results1 is None:
      8             continue

<ipython-input-42-9f17a4d1b584> in skills_info(city, state, job_title)
     89                 # Now that we can view the correct 10 job returns, start collecting the text samples from each
     90 
---> 91                 html_page = urlopen(current_page).read() # Get the page
     92 
     93                 page_obj = BeautifulSoup(html_page,"lxml") # Locate all of the job links

/Users/justingosses/anaconda/lib/python3.5/urllib/request.py in urlopen(url, data, timeout, cafile, capath, cadefault, context)
    161     else:
    162         opener = _opener
--> 163     return opener.open(url, data, timeout)
    164 
    165 def install_opener(opener):

/Users/justingosses/anaconda/lib/python3.5/urllib/request.py in open(self, fullurl, data, timeout)
    464             req = meth(req)
    465 
--> 466         response = self._open(req, data)
    467 
    468         # post-process response

/Users/justingosses/anaconda/lib/python3.5/urllib/request.py in _open(self, req, data)
    482         protocol = req.type
    483         result = self._call_chain(self.handle_open, protocol, protocol +
--> 484                                   '_open', req)
    485         if result:
    486             return result

/Users/justingosses/anaconda/lib/python3.5/urllib/request.py in _call_chain(self, chain, kind, meth_name, *args)
    442         for handler in handlers:
    443             func = getattr(handler, meth_name)
--> 444             result = func(*args)
    445             if result is not None:
    446                 return result

/Users/justingosses/anaconda/lib/python3.5/urllib/request.py in https_open(self, req)
   1295         def https_open(self, req):
   1296             return self.do_open(http.client.HTTPSConnection, req,
-> 1297                 context=self._context, check_hostname=self._check_hostname)
   1298 
   1299         https_request = AbstractHTTPHandler.do_request_

/Users/justingosses/anaconda/lib/python3.5/urllib/request.py in do_open(self, http_class, req, **http_conn_args)
   1254                 h.request(req.get_method(), req.selector, req.data, headers)
   1255             except OSError as err: # timeout error
-> 1256                 raise URLError(err)
   1257             r = h.getresponse()
   1258         except:

URLError: <urlopen error [Errno 8] nodename nor servname provided, or not known>

In [272]:
copied_feature_list = [{"geometry": {"coordinates": [-95.46103649999999, 29.737203], "type": "Point"}, "properties": {"address": "2800 Post Oak Blvd #3900, Houston, TX 77056, United States", "id": "4b62e79323dd04edd16f18a3570c6c525c72352a", "job_title": "geologist", "name": "RBC Capital Markets", "photos": [], "place_id": "ChIJMzyxy23BQIYRmQh7_lj7cok", "rating": "NA", "reference": "CmRSAAAAZHCxUrcoNdmNHk-acO8JGRqvdpVGfoaJwc8gocBrMOwPY_kNrdG_voVRQhyobLytDJDE3z4no1B-jG-S1UU-XT65b8VH-a4MgXx5-b2DqbRErnd959mCH-Gbr5Bu7ptNEhA-to4Cld2aG366VDyB5m5RGhSDRAL2FObJKSL8ZwimNGfoWI8D1w", "types": ["bank", "finance", "point_of_interest", "establishment"]}, "type": "Feature"}, {"geometry": {"coordinates": [-95.3640089, 29.7604054], "type": "Point"}, "properties": {"address": "600 Travis St # 6500, Houston, TX 77002, United States", "id": "e6f1fffeaff13624b25a14bca2c17e581e517245", "job_title": "geologist", "name": "Royal Bank of Scotland", "photos": [], "place_id": "ChIJa0oElDq_QIYRxrrhsSUehHU", "rating": "NA", "reference": "CmRRAAAAksP4-7nK7sXWDuwBtg-EXiHWpJP_yUy4amXqPNYGyb47XGiTkyoq1rtlPzPnB2OEQUbHIttoRPqQsIM1Y9ff-P9JUIXDmLQbLAj-bLSYGVYbhbQ0lPwAPj9qlE3rrcg1EhB_jTltDy_44fdiWUeUh47LGhQ1pFYpvYFB75tv6AT6QDSNCrk5hw", "types": ["bank", "atm", "finance", "point_of_interest", "establishment"]}, "type": "Feature"}, {"geometry": {"coordinates": [-95.56025, 29.781615], "type": "Point"}, "properties": {"address": "#300, 818 Town and Country Blvd, Houston, TX 77024, United States", "id": "a674ded7a91a457c3d42b551c5d48886ff6b71a0", "job_title": "geologist", "name": "RBC Wealth Management", "photos": [], "place_id": "ChIJK5dbXLPEQIYRQeq5MViNqig", "rating": "NA", "reference": "CmRRAAAAZcdsVAzSrtHD-Tj0udLhSS0SDH-UPzUPYMeZ3Xha1UzvK8Ppxc1ccMI7rjclDSnWcir1y-L1n0HtkLZgrzndU6PgpPcOwI79VM-azj9OvyJtosgAOuO5JbqgKzGh5ibUEhCR0900CNIPoFVohpI_AcLDGhRyMIElqrWc1Zkyhn8VxH7zj5o-lw", "types": ["finance", "point_of_interest", "establishment"]}, "type": "Feature"}, {"geometry": {"coordinates": [-95.45170759999999, 29.7477721], "type": "Point"}, "properties": {"address": "4400 Post Oak Pkwy #2400, Houston, TX 77027, United States", "id": "ebe2836d9d530f6081066f7a4aed3a7d4066d74f", "job_title": "geologist", "name": "RBC Richardson Barr", "photos": [], "place_id": "ChIJX1ZfCT7BQIYRrP8hSoM5Mpk", "rating": "NA", "reference": "CmRSAAAAoFk_baD9zBngvpBzuhqLGLD1R3VjijKb77urDytsLaGcHqyLg0gKRJuowObb6hvn6CbpADCmSCuK_Ntmvxigto9LUgzNCWkaIxZPCaGWrz_q32TDWMzcvDjJBWt3BvedEhDK1etcP722mC7kplFZeSmHGhQN27PHTjczUbck20wmg8_7eKGq1Q", "types": ["finance", "point_of_interest", "establishment"]}, "type": "Feature"}, {"geometry": {"coordinates": [-95.461597, 29.746341], "type": "Point"}, "properties": {"address": "1980 Post Oak Blvd #1630, Houston, TX 77056, United States", "id": "4eedac6f1ba8c81d62786ea3ea10f3686ad5b9d2", "job_title": "geologist", "name": "RBC Wealth Management", "photos": [], "place_id": "ChIJlVxoBkLBQIYRDDHQy3MpT_A", "rating": "NA", "reference": "CmRSAAAA1YorTOPuGmoNXLBvZe027qM6M-kf28IIAEXp69BmpqAqhganReouO6Nc6SutM4unYNBodk8EZIFkLwUPSdqv4UuvjQtSVD7yoip4DMOqzuR_ZSQPMjZP1jQC6md8kbpGEhDXGKhJiJA6OuM_VOHnSFD5GhQ9AEnBaVP7XnJnfbIQ67JhMcXBxQ", "types": ["finance", "point_of_interest", "establishment"]}, "type": "Feature"}, {"geometry": {"coordinates": [-95.36388699999999, 29.755906], "type": "Point"}, "properties": {"address": "1001 Fannin St, Houston, TX 77002, United States", "id": "cd0e0c0273242313933c8043aec4389b3fb9a983", "job_title": "geologist", "name": "RBC Wealth Management", "photos": [], "place_id": "ChIJr9ZsYDu_QIYR8bROl7dKBws", "rating": "NA", "reference": "CmRRAAAACVEOnQqw7dIbAC8kannYNuUPVC2k0V6VOepTzJP4w7xik0_azttSiwPyaFryHIplmnVKaI3t4alQ8N5pjkjaLk4SgMNvwzB5dlXJWih5OvstPoyfRTGK8wrjhj9PZFgtEhAhEf0sRguaQykZvkocerF2GhR4CBJzH9cc9d3H7TtEKRmOU-Y3fA", "types": ["finance", "point_of_interest", "establishment"]}, "type": "Feature"}, {"geometry": {"coordinates": [-95.3599019, 29.7546294], "type": "Point"}, "properties": {"address": "Hess Tower, 1501 McKinney St, Houston, TX 77010, United States", "id": "04c70c4a3d18050ca437bbaedeca70bd9cb01927", "job_title": "geologist", "name": "Hess Corporation Exploration & Production", "photos": [{"height": 1454, "html_attributions": ["<a href=\"https://maps.google.com/maps/contrib/111482964284093817946/photos\">Sau Hei Lam</a>"], "photo_reference": "CoQBdwAAADAsGx-uYzaxWlUYRcDGRkqQsXvJslT-KiIKXYL_ZfuvPnpctDeOJAP2Twjmwh9EWZv98IW9t5ZAKPXNzYIL5yQMqNMhuZfW9ImQd-_-nF2-g_y4ItQ1v7V960m_6DgsLu0cEMlCRIFnzJFBvjedr_NAPQur3J4ZvvXjFue-ktxLEhBDDUD6PSd_Kht31zarvLvFGhQuGlp8eVWrF5Y10-A_x5ge6omCbw", "width": 2161}], "place_id": "ChIJfy2iBDm_QIYRjgKEE3GFL9Y", "rating": 4.4, "reference": "CmRSAAAAyjqRBy1c1Gl9pVkQO55DOWnlufEOpBacjpDiMWE9Nhq5it-vGlmjyOiaWfl22foiZTngB4QB04OFlLYF9AkpUuqlPxtxWhq6GDkruNKGA3IBFS58fQReTZkxZW64SOLxEhC78Fkoh_OKppDszKIhXz7OGhTiCjCr3EtrFQET5AbHpoGot4_hDQ", "types": ["point_of_interest", "establishment"]}, "type": "Feature"}, {"geometry": {"coordinates": [-95.53667899999999, 29.643324], "type": "Point"}, "properties": {"address": "10710 S Sam Houston Pkwy W #3, Houston, TX 77031, United States", "id": "21ef45fcadb15a9dae92a34c0882930987cfd934", "job_title": "geologist", "name": "Tolunay-Wong Engineers, Inc", "photos": [{"height": 785, "html_attributions": ["<a href=\"https://maps.google.com/maps/contrib/100502235174758387817/photos\">Tolunay-Wong Engineers, Inc</a>"], "photo_reference": "CoQBdwAAAArT1CGFRoNZlFj7WQjUXK8QliuPYYi0ukbmGisMoj4h9t5BDd20oeOfjQ-6BhBtIR66MyTx7cLCQR3Dsc1OtnxU6uqD9Zd7lILGYyrzHSX91Fa7Qz8EOGg-_CH4xVGf6dUnbEdqDy7WHZoKwadqEu3x_Bd3J1mLbkFLM6MOtdxAEhBa9c8gJcMW8-hVZraN4NrpGhTeX4STpG2LelsRPEeP2Nd_mJqT_w", "width": 1791}], "place_id": "ChIJgd3o6kPoQIYRBdEf5LXmjLY", "rating": 5, "reference": "CmRSAAAAM8g47276syZWm3MUBgnjg6htvM_G4JNfTnO7UQG5cGZNUG4ph-dPjjtEy9CKA379yU67_AX3ZkEgMQ5KXFg4U5JywdB0mAzt5lsbDk-eCw_g1JHyFhHucRLf2ATtXJA0EhBTc6rjFTKJol2OR7vhJ3iqGhSKPbBcxsnIJn8qV1ieX2N2TbMnDg", "types": ["point_of_interest", "establishment"]}, "type": "Feature"}, {"geometry": {"coordinates": [-95.4620181, 29.7530878], "type": "Point"}, "properties": {"address": "1360 Post Oak Blvd #150, Houston, TX 77056, United States", "id": "9aba7fe2f8a80c94b359e1fd5c4df4b3c3e70314", "job_title": "geologist", "name": "BHP Billiton Petroleum", "photos": [{"height": 1724, "html_attributions": ["<a href=\"https://maps.google.com/maps/contrib/106919442231730187134/photos\">Chad Burrows</a>"], "photo_reference": "CoQBdwAAAG3bCPXw7iKaUG4o8aFuoAtfOTpTBN7ohWBOjyOfuu6IQA7guxb5xbBHoMfDVna9zRYFS-wJdyNM-RbFCP7eYU-5L0G61HdFBPDWEygzPeN2LVRJqfzXdBiPAQsP-Dem0Demm86xDUG7zdPDr1ZwQdUjoN68LiskJ6M0o1C_32dSEhDb80JgBRumf-2Dc1vGpUVoGhRxN-dDL89DmubVUc0AEVNkqd7moQ", "width": 5502}], "place_id": "ChIJU5hfp0bBQIYRKqHNd5nxNbw", "rating": 5, "reference": "CmRSAAAAOtuDI97DSC03CfMFYMeMM7Le4JVH32Ue_zzO5kvfAyiE4iB8sv2lsI_-nGP6NTYxC0-cLgLk1xKCcsTIRKK54AnR0--cAx9tIIGzY-e3AP4TgDIU0A2-1lrajGV4L9fxEhCdYg1w1KdB43tyM5fl1LonGhR9xxRxy2aLuY_vyoK0hOS5VjHMMQ", "types": ["point_of_interest", "establishment"]}, "type": "Feature"}, {"geometry": {"coordinates": [-95.1974345, 29.658069], "type": "Point"}, "properties": {"address": "1006 Vista Rd, Pasadena, TX 77504, United States", "id": "69a96533a258eb591726d86d1ca2f9c6ec0228de", "job_title": "geologist", "name": "En Rud Resources Inc", "photos": [], "place_id": "ChIJc_A7nUSYQIYRcN8s1islssY", "rating": "NA", "reference": "CmRSAAAARNn7XDmBjchus_55SmPZ5TmGnW7ArXqyAQxN4TgOLGP25tcDU8f2gTvRAIiN9u1d5gbYaBRUoTB7srB9y-2X7juZxovmAIefNQt0qRCCcS8xORxkF-I1j4rF8I9IY-w7EhAqQwfsoQ7OwFTBZHTEwPJcGhTtR6GTosBmPdYpXthBzXDr6knVuA", "types": ["point_of_interest", "establishment"]}, "type": "Feature"}, {"geometry": {"coordinates": [-95.1721678, 29.64837929999999], "type": "Point"}, "properties": {"address": "4624 Fairmont Pkwy, Pasadena, TX 77504, United States", "id": "9ae520cccc7564f96afd46f6d631d61bdd6bdfff", "job_title": "geologist", "name": "San Jacinto College - District Office", "photos": [], "place_id": "ChIJ5czzhuSYQIYR5xO1zKMXD90", "rating": 2.3, "reference": "CmRSAAAA4L4AmA9IycF2CT257U_Hh7eozu7eVLnC9T3GlQw4NtraevdReLy38PMYFI5IwwYPfrq-MahL1SrJynGVETVgaaSfogNOhbCiIYaIXhpiCt99j3M_f6j7e1ag1muR_O9fEhB2bxYUhExHFmwkvWaNpYTTGhRm2YBVNSsg1RuZnnPOlyyhsQ1_Cg", "types": ["school", "point_of_interest", "establishment"]}, "type": "Feature"}, {"geometry": {"coordinates": [-95.366643, 29.76074], "type": "Point"}, "properties": {"address": "700 Louisiana St # 2100, Houston, TX 77002, United States", "id": "ec8b82b104863bab3b36a1ce79a0c0f711468bfc", "job_title": "geologist", "name": "BMO Capital Markets", "photos": [{"height": 750, "html_attributions": ["<a href=\"https://maps.google.com/maps/contrib/104549896185334272100/photos\">Duplan Nalpudi Instagram</a>"], "photo_reference": "CoQBdwAAAAJ6XTFHXEE0Wadaxe8OTluFE7HUrb0Hq_EBeBBivWEwG6vKOzetGq_2z7PWILXcRQy_EIbhdSPZK2vbrxRHH9IFCS14fkscmI6RNIPFXi_vSGjA1-YMMP1QmIeNlfP2W3_hTd5Ay8If866LrdeVmHM1_tLMRs1u9rYHR0tQNTDyEhCzS3KITjIfGZJIXYxmW41QGhSeJURd4g9XdNAeTX8C48oWmAXjOQ", "width": 1334}], "place_id": "ChIJLROgDTq_QIYRTwQmXrl5Wm0", "rating": "NA", "reference": "CmRRAAAAxnASvDFOUjGrpkDYDWmqNrv5OaQE8PPMqfWuJsESxbIPLkcapX38R6GqZmBN9EqoPAJ8eFC15N7smXVcNe3avTJYlmaRh7i34FLRAD-6ak7H_zs5g401_5P1MFqd-MCtEhBrI68CWVZNFxuNb2weMXfTGhRj8jGjRvBUfk5gIjIeU-NqkPS5mw", "types": ["finance", "point_of_interest", "establishment"]}, "type": "Feature"}, {"geometry": {"coordinates": [-95.372164, 29.757501], "type": "Point"}, "properties": {"address": "333 Clay St, Houston, TX 77002, United States", "id": "795a3515ff023985c96d55d60c8eefcdc6c9ee0e", "job_title": "geologist", "name": "Jefferies", "photos": [], "place_id": "ChIJe81fkji_QIYRhzwdUhh-ygw", "rating": "NA", "reference": "CmRRAAAAyEvFORruDkPxY6ltJiQcOqA9ih16L_Bffm7-I-zSf8p24oX3ggzEZxXflRPr0MkIbr-8CZPbrKTBX9ldF7ApeJhHCf-yAXZr0Q-wKPqacQFS2LftiUsbgGRwZ10fq8CBEhAI8nEAl2mIFQhwWyUpwknyGhR6dWz7jSHNRyWRwkpalAvStqE-SA", "types": ["finance", "point_of_interest", "establishment"]}, "type": "Feature"}, {"geometry": {"coordinates": [-95.49726899999999, 29.7140059], "type": "Point"}, "properties": {"address": "6100 Hillcroft St, Houston, TX 77081, United States", "id": "372e0791c5d5ea0bf4c3a24c278c5083aad17624", "job_title": "geologist", "name": "Fugro Consultants Inc: Akhtar Anwar", "photos": [], "place_id": "ChIJ5e-dPzbCQIYR8o0_0WHFuVk", "rating": "NA", "reference": "CmRRAAAAJfSbIwfGz4EogbvyegiWN7kAXAqG-eCvMKewYZtyW9qGnal_gIO_Muj_4gwxWz3-_IQ-R4zMI2pDFS3Hj6dLv4vqQGbnTjQd4HUVCHIuXuxqFjKF7xJpNy722nji4ElVEhDXLF1LrlDT4a3IlkXq-JDjGhQPorvUROrFmF4T1ejh9270ZKgk7A", "types": ["point_of_interest", "establishment"]}, "type": "Feature"}, {"geometry": {"coordinates": [-95.5678336, 29.8452744], "type": "Point"}, "properties": {"address": "10831 Train Ct, Houston, TX 77041, United States", "id": "94c4bf4197969258554d1555fd7ce686908546b7", "job_title": "geologist", "name": "Fugro Consultants, Inc.", "photos": [], "place_id": "ChIJ1WVb4rHaQIYR6O9DfGla99A", "rating": "NA", "reference": "CmRSAAAAKZUmGmU-bf7JcLeqY4CoAO4bJOU9BWP1WCw87_vXy-_3agr7LZX3mch5WO-iWqlEqkZsAePSh7Lk5AN7BILjLmAew1GbqUoG_JPT-k5aDxcFNWdwpJciOb2BwN5VV7dHEhBoD9R3HF4PMvor-5dmDx0zGhR0WBaFdbCL5QEDKypbe9V5mVMSog", "types": ["point_of_interest", "establishment"]}, "type": "Feature"}, {"geometry": {"coordinates": [-95.5441765, 29.9263062], "type": "Point"}, "properties": {"address": "8715 Fallbrook Dr, Houston, TX 77064, United States", "id": "4b8b00e13f61a661128d24dcd3068ddd462bddbc", "job_title": "geologist", "name": "Fugro", "photos": [], "place_id": "ChIJC49COz7OQIYRAkBflL00eJ4", "rating": "NA", "reference": "CmRSAAAAKnJ-PLXUz2cGuMXBqlupgPuRmIx6br2jerJOHQ3PnCMCu55xBuGY8L0U1eAO8sSteu3nmHbDVGVgstxk-rmM-VLSZlwkm1n3H43KdgX74rVcp7X52uM0WGv-49M_qALbEhBU-hqOBMDdyEaTaiUxIIE_GhQOwIsvKrQrYjHq9q5b94aoR87I2Q", "types": ["point_of_interest", "establishment"]}, "type": "Feature"}, {"geometry": {"coordinates": [-95.4994463, 29.7127126], "type": "Point"}, "properties": {"address": "6121 Tarnef Dr, Houston, TX 77074, United States", "id": "036ef56e28e7616b45367256404bd34b6894d17b", "job_title": "geologist", "name": "Fugro Inc", "photos": [], "place_id": "ChIJ1ZxaK0jCQIYRkHmkjNdFW2I", "rating": "NA", "reference": "CmRRAAAASHUZ9MB81iK2MLEhgOYZ5Eru9ekeNs_Vl8F91I6mVP3MX5_ce48QOzNfpxbB74_ctpGO1q_B3m8E8herIETMU64Y9ACmVO_HjXTq7cEHCWkl8TpOkJrLiYA7R5cRglE3EhAVDmbN2jituXKBsYShQRzXGhSJHn5bD7k3BQxxX2w2x08kBUtNgQ", "types": ["point_of_interest", "establishment"]}, "type": "Feature"}, {"geometry": {"coordinates": [-95.49562680000001, 29.7167202], "type": "Point"}, "properties": {"address": "6080 Hooton, Houston, TX 77081, United States", "id": "65dd391d8d93517cc6dbcdc22dc4231b9aa5303c", "job_title": "geologist", "name": "Fugro Inc", "photos": [], "place_id": "ChIJrdJGMjTCQIYR03_Oibwj_uM", "rating": "NA", "reference": "CmRSAAAAowhSnsCeJm3gYOnEDNZ7a43E-gqlh62gNyk2xMRNqkO9GoQszFgAI5RFPL8zCrlgZAdbgyqoPFlmMVqxvGGkLT6by6pTBuN0BeT3C-L1AD41SfUVOy4NiTG7LHNngnguEhAgJX7Xs8ZVeX7kSXgb14npGhSlkRKhK8KPDxnrwSC9OPxAoI-36A", "types": ["premise", "point_of_interest", "establishment"]}, "type": "Feature"}, {"geometry": {"coordinates": [-95.5503257, 29.8584718], "type": "Point"}, "properties": {"address": "10425 Okanella St # 100, Houston, TX 77041, United States", "id": "bd7b9e455e61e36012f43900a5d2dc8fb520b286", "job_title": "geologist", "name": "Fugro Data Solutions", "photos": [], "place_id": "ChIJf7sDHvjPQIYRNi_3faTzFrQ", "rating": "NA", "reference": "CmRSAAAABMsN0BF4qImRGXhbd9C3pv5Wpuh-qu1oMpNEsG3IrcMLS9g_2trO-QYxZO-PhzmRqzVXFSRO26iD97rvlaU-OicQK_eO2rIkbAGxqqQXLhrIelEF4-iFbH98WgNl5z8bEhCueCT4nussffuXOMwuSymqGhS7CJHFuQ8i4pzMsHSL24DrOdjSZA", "types": ["storage", "point_of_interest", "establishment"]}, "type": "Feature"}, {"geometry": {"coordinates": [-95.1800995, 29.7118821], "type": "Point"}, "properties": {"address": "2410 Pasadena Fwy, Pasadena, TX 77506, United States", "id": "38cb6e415101a4bac2c1eaf17a6fa77679f6788b", "job_title": "geologist", "name": "Fugro Consultants LP", "photos": [], "place_id": "ChIJQdSxQV6iQIYR9uoIbHWfBXE", "rating": "NA", "reference": "CmRRAAAAgRQU8gFQoDoGvfZONgFJ0L3TE7-2iinmImlY2HSudOYS_Z9PG8bUuZeql0kJn-HnUfS7S12okDg4LlsBofHxRZp8I1wUNbp8PkV9K2nC4wMRC0NaG7ow8FLyopwm0hRtEhDIEHytQwc3dPTnnxNSqkNuGhQK-5zmh5oXjG0Xyyo2LYd_VqRMEA", "types": ["point_of_interest", "establishment"]}, "type": "Feature"}, {"geometry": {"coordinates": [-95.5740797, 29.7373078], "type": "Point"}, "properties": {"address": "11200 Westheimer Rd #365, Houston, TX 77042, United States", "id": "328101c9c23ad52a56a549ad72e19915b58d7af8", "job_title": "geologist", "name": "Walker Elliott", "photos": [], "place_id": "ChIJz6iXr8HcQIYRnzHDA7T8m-k", "rating": 3, "reference": "CmRSAAAAq3X0LE0-YJu5gH53VpxVHV1FRyfgqS5Tbzy9VOevK-OPO0E0edNWw5saqHYmTQeI13OrCRRn55IXCNR-twRG4LP9H4OLloCM1sXuLd5QKQfMBm1vsQJ62ahiFOynW3k9EhAnqQFCzrgoaAj2O0GjiknZGhT-CTEzUydto4xQHLi6leHqjz8IrQ", "types": ["point_of_interest", "establishment"]}, "type": "Feature"}, {"geometry": {"coordinates": [-95.3662701, 29.7561894], "type": "Point"}, "properties": {"address": "1111 Travis St, Houston, TX 77002, United States", "id": "6cf1f2b19f724b7014c7cab1c01725834dbc3db4", "job_title": "geologist", "name": "Hilcorp Energy Co", "photos": [{"height": 2448, "html_attributions": ["<a href=\"https://maps.google.com/maps/contrib/100318015046809414765/photos\">Ronald Payne</a>"], "photo_reference": "CoQBdwAAACD4TuMx3YdUMuEMttal89_H2i4a_Yb_N8J84PvSwa6P7yZIPVzHSgLp0rVq9wVisW1zylOPPewgCqZl6wr9wB0CM8oikmhhBNk63khPmUvev2mLkGW1mnm1FE8hL4zqpLAq8mpxmVjo4VXFsg843Vhn6wmTnykgHrOvGdiL21RwEhCbTDT6gPAjAyW_adOD4KfvGhRWkL9T-I38Se4XCduhw9giN7lyaw", "width": 3264}], "place_id": "ChIJncGsRDm_QIYR0e57PbvugTc", "rating": 4, "reference": "CmRRAAAAR5xWpcIzDmwYtGOFcalgmHc9XTor2q_3GqgNBVbk-rIr9uOmpMFBfQ0rL3SO6sPVxjD4tLB0DzBSy5SdxAUJhn3WNEwdyz3Db526ujmfe-cO5iOFp8TQBWRJbXf4yY_aEhCjB73M7KtpHi8zSO7Hd1LHGhSIn_gKCLWU4j1Fho5aOjPkuYkMUA", "types": ["general_contractor", "point_of_interest", "establishment"]}, "type": "Feature"}, {"geometry": {"coordinates": [-95.4321022, 29.7305064], "type": "Point"}, "properties": {"address": "5 Greenway Plaza Suite 110, Houston, TX 77046, United States", "id": "7394562c1f1a87dc4b6fa017b44a961df160f5ef", "job_title": "geologist", "name": "Occidental Petroleum Corp", "photos": [], "place_id": "ChIJjd5k24G8woAREjjHjBsq0Yk", "rating": 4, "reference": "CmRSAAAASz86jQdTDOwlIvwdnA3Qz8xUhez7ibpthJLs6BCJvA22JiaWnbdsJFy60jilcgoM0tpbN3i8KywPW5oMHvzxeGJM3LU3vSeg5MJRgwCKCL_OCqpGZllOudVGMM73GshlEhDVbtotSzfF8JxecMlatoslGhRp2Fwf93AvjW-Hj7Homm7sQj7oEQ", "types": ["point_of_interest", "establishment"]}, "type": "Feature"}, {"geometry": {"coordinates": [-95.3970411, 29.9417677], "type": "Point"}, "properties": {"address": "363 North Sam Houston Pkwy E, Houston, TX 77060, United States", "id": "bcfc0554855f942f730466fd447878511b6aa0b4", "job_title": "geologist", "name": "Occidental Petroleum Corporation", "photos": [], "place_id": "ChIJx73rqePJQIYRPjss3jFElZo", "rating": "NA", "reference": "CmRSAAAAhuoL6RZDwAgakjHAPkQ70yt-z6OkbCizb8q-DZhXu4VSVrqxw-9P1Z522eoJLNvg28otlNy0gfxz8RSdtk6_MVVmvbH_PrQiIAWCIzsxJGgLYBqO6wh-rYaQ8D6Qnr8kEhC2y74j1TpWgjqBhkoWFQXyGhSffVxx7DkI0kLRszfjmBpxHWXhBg", "types": ["point_of_interest", "establishment"]}, "type": "Feature"}, {"geometry": {"coordinates": [-95.5498597, 29.66888299999999], "type": "Point"}, "properties": {"address": "4301 Southwest Fwy, Houston, TX 77027, United States", "id": "6e40f1d16226178cc0cf90f68d007ada7cfe5617", "job_title": "geologist", "name": "Oxy USA Inc", "photos": [], "place_id": "ChIJj7uu3g7BQIYR1FyPVqiuar8", "rating": 1, "reference": "CmRSAAAAmEUCNeVc4zYeUcO3FYggAj1XDwroO90SL-bxT75fmTME5_iVd377kIQmhSdMrHrEWxyiU3ooZGVVjAnEqAnKU055hS5Jw9FjceJqbZqevK39LAgxXXVco9W1Y9Fl70-lEhC6j0QARdoZ1vWdm-jQ3M6sGhT5xXZn0-bzlUcIc7yrGTUwkfRXag", "types": ["gas_station", "car_repair", "point_of_interest", "establishment"]}, "type": "Feature"}, {"geometry": {"coordinates": [-95.5438387, 29.7776847], "type": "Point"}, "properties": {"address": "800 Gessner Rd #170, Houston, TX 77024, United States", "id": "91282085c6930276af6f7e2abf1ee0e0fc18432c", "job_title": "geologist", "name": "Murray Resources", "photos": [{"height": 683, "html_attributions": ["<a href=\"https://maps.google.com/maps/contrib/106500950429449697681/photos\">Murray Resources</a>"], "photo_reference": "CoQBdwAAAFemj3kmrLnXYfPLodQxo5ElybQv0GkKavHa_44R-FibcTwjLE3xnJqBOVAXU_mwTEjQ3lQAzZ3nAhI_G-3-miEKPAqCWv6hujQV-DbyoXyUQ5wo-7_-rC0IKA4pp9l0k3cIKzZo-zTxE2B9D-a6zZMMN_BMnKH5x17GXA3bkgFvEhBZI3TaZ9CQN7454CvQeDuaGhQsBW--A7BjExS_YRHi0pXA_NslvQ", "width": 1024}], "place_id": "ChIJRSYpxLzEQIYRsKFA9Ahm-Z0", "rating": 4.6, "reference": "CmRSAAAAt8uZVNFLsZhKkIklOc3Wt3UL4i9ODr6P4gfKwLgUwKriPq-3BEX1keue__3Ln_57cVzDGSnrGBy0C4i2yYDBpKzRg2nDmA-MDpidWSGseEnsgC2T4Tj3E7i7bTG6Vb48EhAGh5UF-BJ_JIoZsGL08p8iGhQD3UQOpAbsKoGsdF7XlJjkykBh-w", "types": ["point_of_interest", "establishment"]}, "type": "Feature"}, {"geometry": {"coordinates": [-95.411982, 29.838328], "type": "Point"}, "properties": {"address": "707 Lehman St, Houston, TX 77018, United States", "id": "e3a902a8d57c6ee9d36a8e1a32fa39c463a33a0c", "job_title": "geologist", "name": "Intera Inc", "photos": [], "place_id": "ChIJI-1445THQIYRvn-6mbb_i8I", "rating": "NA", "reference": "CmRSAAAAjMFpeODpK4DnExOwKuas0jsuXqbP1uyqyvt2I7lDsxE8H6wdt4GeLnF3WpZTmhNzX8XaMh9zktB4PRRW3khfr9aKWyHQkdDdsZYLLj6_TydX0GS0j5POQ83q1SkA-cj4EhAgpn3QZGXi92tnkS7QDK6uGhQmpNusZ0uoD9L5vrwTJiYidnHgSg", "types": ["point_of_interest", "establishment"]}, "type": "Feature"}, {"geometry": {"coordinates": [-95.3574139, 29.8867077], "type": "Point"}, "properties": {"address": "11939 Aldine Westfield Rd, Houston, TX 77093, United States", "id": "596dee2eed3253cb2fc6ebf53ac71041aa3694f7", "job_title": "geologist", "name": "Weatherford", "photos": [{"height": 2988, "html_attributions": ["<a href=\"https://maps.google.com/maps/contrib/107786689521565648284/photos\">Donnie Scott</a>"], "photo_reference": "CoQBdwAAAPBqgpJau23JGWsXP_aHT2dZ0z6KNpoGUZcFHUQooyiDqK2DTxBjYbTlPN3zY6r6RUJ6DSpqhAP509_QDUFJKIDgU16rpOmH2-dKijS_TyTlMKoLAaQSyvgJZUqZN1MdLdDtOM_DeR2dUo1Z6zlCSLpWvyMO0RvtcvwgKR-MG3wiEhAzflC8VBBqexJpo763_wKyGhRYW4LyCA1VYpi_0dgsU8iun9uAqg", "width": 5312}], "place_id": "ChIJJTOHIp-3QIYRLKxLIjOV8yk", "rating": 3.5, "reference": "CmRRAAAAszrI9qFjAvDkRZHAlfYcvBlgyGFY02Yn1xwQC3DyDlUrZUlLrCnRa0gxaiIF_gZ5UOCmm5X4UwcqL1VqZa73C70WPifaxR2ep5pRJ5VOeC_njU_SlJubAWzh1m2mIiTdEhBrqSrS-vOnX9_K3M9vT2iQGhRL2k_B3y8OnhNz4N_AwvVFEmLEvA", "types": ["general_contractor", "point_of_interest", "establishment"]}, "type": "Feature"}, {"geometry": {"coordinates": [-95.47312559999999, 29.74571959999999], "type": "Point"}, "properties": {"address": "2000 Saint James Place, Houston, TX 77056, United States", "id": "52afd1ae1d4a85581d56feb80c02e3a0f203e7c6", "job_title": "geologist", "name": "Weatherford International Ltd", "photos": [{"height": 5312, "html_attributions": ["<a href=\"https://maps.google.com/maps/contrib/109977538253417550023/photos\">Toufik Djeradi</a>"], "photo_reference": "CoQBdwAAALEJd3HLtOFVf742uAUKfcWbY12zZLviR42hY1WctUwxrabZhWal2JR2pBP31fD44TTTvazBySu69YtJeMhLMxcz_E99YbxXe781BCYCab5ZzyeVWblcKVUoJ-zuzWdNLka2puviqeGFXQF02yzXQZ0LSij5nnmTB9wDRDl3s7TTEhBsFAtQlnvtj0D0xwshAcO3GhTFfXlAf0fVNCFrfEAUN2JlrzZENQ", "width": 2988}], "place_id": "ChIJ4ZM-A17BQIYR6GEbiv0fqjY", "rating": 3.8, "reference": "CmRRAAAA0S8bhOc5AkWCHfkYXa-8GTUlGY4JanIPmTlYfPWAGl3iEX9eaYNLKe6RSO8lNSFmnn9psfeWPY8-R8gfjAr0u6dFzgox9nh4x4OG9wg7OyfFnQFJba0VcHbFazmlGQ3LEhAkWcdb5kxLYW4qbs0Mym1lGhRgVsmkE-hBMRISasdiXPMjJPsREA", "types": ["general_contractor", "point_of_interest", "establishment"]}, "type": "Feature"}, {"geometry": {"coordinates": [-95.4008035, 29.9623403], "type": "Point"}, "properties": {"address": "18160 Imperial Valley Dr, Houston, TX 77060, United States", "id": "4d3095b9bb6426aacd6c3a9290d25e7a1271e552", "job_title": "geologist", "name": "Weatherford", "photos": [{"height": 2268, "html_attributions": ["<a href=\"https://maps.google.com/maps/contrib/103289608261407307137/photos\">KEVIN THOMAS</a>"], "photo_reference": "CoQBdwAAAFkUHqa-ujnW7m_GyRGOsFG5J2zTbQLlbhT0hFJD1W6oVuYrAVbBvQUjxPfyZYaPdBfsMznpVBkwljhPWsEQffrfUt1FZP781ZcS2dSz4z1sjhWfoy13wz2RuhXftdP04xiu8I5p1eEiucMmArsUtIbt1xI-OAOYi71SkQqi1f74EhB6bXxL2tCY1EOfBbm7r0ufGhQHId0-JKkc804PeKHtTtkUYl7y0Q", "width": 4032}], "place_id": "ChIJ0-giCwTKQIYRcRakt7fNf8Q", "rating": 3.5, "reference": "CmRSAAAAg1YoqU8G0Mvx4FMNxoA3twXlk20iaACySpBEAPk6wYCCXaKhSB8MaBhj7N5XeqWHELCUBvolDsarzM6v50xMGU-1Hax_5ue18KgRm29GABrj0w15DN-UUHRGK9hqj8BKEhC9n-bnAqSHI8AXVvcz3AbnGhQZbJrYst_4BFnMVfb1O_Xodzy_kw", "types": ["general_contractor", "point_of_interest", "establishment"]}, "type": "Feature"}, {"geometry": {"coordinates": [-95.59471649999999, 29.8775974], "type": "Point"}, "properties": {"address": "11997 Farm to Market Rd 529, Houston, TX 77041, United States", "id": "952ed47a8b304b500d4c7fa4b2f7acc9d81862d0", "job_title": "geologist", "name": "Weatherford", "photos": [], "place_id": "ChIJN6mSK2jQQIYRsomU7nEAtQo", "rating": 5, "reference": "CmRRAAAA-t6v6dX4zv_WrZqHf2TqiE3366W1QBzJE_Rw4vDukPPEi2Xd9FUT1d8As_530LtVxZuL-tgEIXrdReMXuK-NRlpP1fcc6HlwP5jLltUnTNOFx2tYsLjDC9jfrlTFgq7-EhBs8VeTJ4uNzFS0BQm9RBHsGhQ7ainQBAbT4n2AiK118M2zio1ihA", "types": ["general_contractor", "point_of_interest", "establishment"]}, "type": "Feature"}, {"geometry": {"coordinates": [-95.50646259999999, 29.8392312], "type": "Point"}, "properties": {"address": "4409 Clark Rd, Houston, TX 77040, United States", "id": "5897514914025020b16834cc3321b79cd91ddcf4", "job_title": "geologist", "name": "Weatherford", "photos": [], "place_id": "ChIJRavrVZbFQIYR-V3u4J6Px6g", "rating": "NA", "reference": "CmRSAAAAs0UsPlWE2YHivzNIhYeQOD3TfOHJVJhxSPpDZvIOb-FrRJ5zHwfDqMcT9nUkVZt0LhZikWEl83dLKmJMYQvOjENeJChA7IV1gkeoE5EgfWPO1KO5JW0Zj-3EfLz5X_5-EhBRBfg-qJMiazKTtLIZkuX9GhQvER37KjGNIJW6GmiByot2Kr6M3A", "types": ["general_contractor", "point_of_interest", "establishment"]}, "type": "Feature"}, {"geometry": {"coordinates": [-95.38671629999999, 29.9536867], "type": "Point"}, "properties": {"address": "16210 W Hardy Rd, Houston, TX 77060, United States", "id": "d8740eea0d7d20abe22e8ee366dc5c88884d8890", "job_title": "geologist", "name": "Weatherford", "photos": [], "place_id": "ChIJaSSBtgC2QIYR1MT_9TLRMdc", "rating": 4, "reference": "CmRSAAAAJeocjUCbVFNTrdH9o7drPGzijbHbjt6V8BmAJ9LHtw3NsL2CmIZx3y7LJOspnUzh-X5V2GTpAN8NsMbnYylkI1a74HAhCdn-__zo7drZTfn2G1e4pidmrztwGVUKlcrfEhBeSCmfWV3qsQ_HK5j7AbnvGhS3toK73knwKZ0kijFdJEahSjj0Vg", "types": ["general_contractor", "point_of_interest", "establishment"]}, "type": "Feature"}, {"geometry": {"coordinates": [-95.5414947, 29.8793251], "type": "Point"}, "properties": {"address": "9600 W Gulf Bank Rd, Houston, TX 77040, United States", "id": "1410b97b0d3e49fac99b37306c2f239edf2cbfcc", "job_title": "geologist", "name": "Weatherford", "photos": [], "place_id": "ChIJIYP0x-rPQIYRQkqUN2zvUVk", "rating": "NA", "reference": "CmRRAAAAv7RdhIoNfr9JmbOql7CSSVTJeJGLhC6PL6zgxR5bzqAeyhFugLsns2qIap-_VGjJJZ2-ySyFqzAFZAeZLqlE5jgz0SUbymucAPg9GUe6teId0ZIrjTOhRdLLps8wUb7AEhCm_Ggjv7O12huk9exoPvdAGhT3I0042XMYziX6EnPpMO7Ptz6gMA", "types": ["general_contractor", "point_of_interest", "establishment"]}, "type": "Feature"}, {"geometry": {"coordinates": [-95.56310339999999, 29.86431019999999], "type": "Point"}, "properties": {"address": "6550 West Sam Houston Pkwy N, Houston, TX 77041, United States", "id": "6af716c199aa85ab00b3099d81170d6589a15220", "job_title": "geologist", "name": "Weatherford", "photos": [], "place_id": "ChIJA--CRgLQQIYRlczuvd0DaDk", "rating": "NA", "reference": "CmRRAAAAnkhj-G6aip3CKIIRHwoeGEwezIyeCoiFJvOz-ndNVYL0ABj0g16nYU5MQb1qB8JqZaj1NCLu5oL-5bT2sbrObRZETpigUA2UtZ_hb9_7GPRbq5hRi7e5BBNAKEVRdgeaEhAU8TqO7vFsY2dVYm6wT0ccGhQ7g9Hz2dD4Ka-umaVuCzY1AtqiQw", "types": ["general_contractor", "point_of_interest", "establishment"]}, "type": "Feature"}, {"geometry": {"coordinates": [-95.32106189999999, 29.95185230000001], "type": "Point"}, "properties": {"address": "4420 Greens Rd, Houston, TX 77032, United States", "id": "0fea99fe6edf1976f5651dcee53a4c65b4b30561", "job_title": "geologist", "name": "Weatherford Us LP", "photos": [], "place_id": "ChIJb4d8jKW2QIYR9DvsxTaZDig", "rating": 4, "reference": "CmRRAAAAE7KQiY2CboLMMOJl0CKP9xFhkOsLaAFQ59I1K7NR8cirR4Cdsuaaa0_Yl7vQ8O3Ch_27HyqW-fsputd8kA3pSWb9Mh2Oea9qcPsOZ5hqyJLKARnsi-mNaQBlkwXm5pdCEhCO9NkkWOgph-EAaM3OYpCZGhRKCzJ_W-Z3jY5RuYaNi-aLyQpSaw", "types": ["general_contractor", "point_of_interest", "establishment"]}, "type": "Feature"}, {"geometry": {"coordinates": [-95.64149499999999, 29.7802045], "type": "Point"}, "properties": {"address": "15995 N Barkers Landing Rd#275, Houston, TX 77079, United States", "id": "487c0f4fad0c96f92333e8445ffb7df4bbdd794a", "job_title": "geologist", "name": "Weatherford", "photos": [], "place_id": "ChIJgWVOPeHbQIYRD310QFCTldM", "rating": 4, "reference": "CmRSAAAAU8keogqpVAUHD7AWz0F9ITOARy1r6Ur0lOQDrylQBdt68ymc6GUAUa5DFRfX2dwioFwKMU5aW33yFD2IzXDb0u101gC_CF2r0q82l1EMdpffDlJ-_pduvMFE3N1W--dGEhCA2GDT0fYmCAXQm5bssb0QGhQrEWUn-rYUH6ZMhaeKV3jADFRm_w", "types": ["general_contractor", "point_of_interest", "establishment"]}, "type": "Feature"}, {"geometry": {"coordinates": [-95.46547729999999, 29.82209649999999], "type": "Point"}, "properties": {"address": "5151 Milwee St, Houston, TX 77092, United States", "id": "7c57cdc787545fb5cdaa2ec867964d2a4a03a214", "job_title": "geologist", "name": "Weatherford", "photos": [], "place_id": "ChIJf8uI6mTGQIYRT2uM5UPk9Rc", "rating": "NA", "reference": "CmRRAAAAp3nIDNOuuZsVDZUKZhANxArKQQbabBka0V4E2Kld6_UtXxN8qao36-BosQjkaIZr-i_NKpm-fvF03DPGXujYnHD9HQKpNJIKDz42-wdo2bPVN6OQa_RL6YmhOziPZt65EhDtLw7BtIwuFGwMjVqN_6N4GhQjnParM6cW-G317chu0lwMM-O-AA", "types": ["general_contractor", "point_of_interest", "establishment"]}, "type": "Feature"}, {"geometry": {"coordinates": [-95.5687557, 29.8280322], "type": "Point"}, "properties": {"address": "3600 Brittmoore Rd, Houston, TX 77043, United States", "id": "292fb3ea5cda6a1e89be2a7e1edb634766ad609d", "job_title": "geologist", "name": "Weatherford", "photos": [], "place_id": "ChIJYxAfN8naQIYRx5yd_B1HBy4", "rating": 4, "reference": "CmRRAAAAj6kpiwfDhdpU4xO_jhItviA-VK-xsI76T8V3mOFCt6tVJO-zjPH1WOl-0xP1EGZ37flL3gl7oDhQm_9zM_YOhQLR5MROW5t43VxYarA8So2HW5O00mXoYidGsT17t-TdEhBWZza9es0FtzyXvQ9fA_UbGhR4raL7nfJPESqs_v5CZIg9PwJKJA", "types": ["general_contractor", "point_of_interest", "establishment"]}, "type": "Feature"}, {"geometry": {"coordinates": [-95.3308448, 29.9467059], "type": "Point"}, "properties": {"address": "15710 John F Kennedy Blvd #700, Houston, TX 77032, United States", "id": "8c57b1d23f4bbd0979cfdc9220021c397e740316", "job_title": "geologist", "name": "Weatherford International", "photos": [], "place_id": "ChIJ8QvAT722QIYRFoA0kAAlp_w", "rating": "NA", "reference": "CmRSAAAAZXryF4e6y1BLozdnMdoVPv3zIWkeT8d1FjJaiZa0avqKA-qtVIwQd6rAI3YkmYBgPzxmi5Oq8KMDl1WO4rxHbXbiLy7qH3V5aWWfDDo6mWL95nkicFs838GmJAMgLIFxEhC8DITwAz4GIN3Dd_GH1_MKGhS4qpkH01Wi_iy9Qj8ourRmXRgQxg", "types": ["point_of_interest", "establishment"]}, "type": "Feature"}, {"geometry": {"coordinates": [-95.49729029999999, 29.9313766], "type": "Point"}, "properties": {"address": "10655 Bammel North Houston Rd, Houston, TX 77086, United States", "id": "ac2948f51dcbeb1d0caac8d3e79696ff62bb54df", "job_title": "geologist", "name": "Weatherford", "photos": [], "place_id": "ChIJ97T_sb_OQIYR3VDC1vCO01I", "rating": "NA", "reference": "CmRRAAAAE76pqgyOJN_IpUjSVkeQyDMjtR0H4OZ7Wmu2OUrVP4HGaAQXiwPNUXa_0dnqdZMT6CmRkEkk5MlrTmecIO0rzlOPfgWh6sn54h8c0QjJuPhClTfM0vB-8CoM-Ol89O5pEhCpqaekiCydnLUiCV2dTdUqGhQ5r04kwX9tLifMzsG1PpCPHhnbvQ", "types": ["general_contractor", "point_of_interest", "establishment"]}, "type": "Feature"}, {"geometry": {"coordinates": [-95.5036944, 29.9384892], "type": "Point"}, "properties": {"address": "5200 North Sam Houston Pkwy W Suite 500, Houston, TX 77086, United States", "id": "c35235ad15c043ae6d3fa786e635bdc00ba7e525", "job_title": "geologist", "name": "Weatherford Labs", "photos": [], "place_id": "ChIJbarkM5fOQIYRtdFDh1I4Ibw", "rating": 5, "reference": "CmRSAAAAH9Mukgmsk7StTBpws9GKPPQnIcUBh_fWcmvEIXmH4Ez23dfqYI1uMkv-e_2Rl1F2I_us3TTap7WenxG2IlBEoZG-78vqxGElQBdh7QJCxPC3RRUGhuCQQF9jAh1zUSfwEhDZ_X8htO81DKQAlNLlRGl7GhQ5-e-j6Sn_ESNyknwXycz4mSidUw", "types": ["point_of_interest", "establishment"]}, "type": "Feature"}, {"geometry": {"coordinates": [-95.58365099999999, 29.87864769999999], "type": "Point"}, "properties": {"address": "11909 FM 529 Road, Houston, TX 77041, United States", "id": "34a35815f125719e685a25e281877fd0f3e707dd", "job_title": "geologist", "name": "Weatherford", "photos": [], "place_id": "ChIJN6mSK2jQQIYRkXRkecpsqOk", "rating": 5, "reference": "CmRSAAAA_RhQ4VNwdnRGWmgBoC5AGqailMLV3RPkolV7pHTbC_YFZ0qQ5gPlRg9DF73_qaO9RyuzG8wAAKDITHsmieRKlOe3uCQ0MqveAxJRjpHJO_rVV6X4Cik9Zel_SDjJGMULEhBQ1msakpPSzyl-HmjOU8cVGhSQVumb_UB_5fbd-0TmBg2d02LwYg", "types": ["point_of_interest", "establishment"]}, "type": "Feature"}, {"geometry": {"coordinates": [-95.551149, 29.9230152], "type": "Point"}, "properties": {"address": "8845 Fallbrook Dr, Houston, TX 77064, United States", "id": "6012e90f06cdf2fc9891b68f8e37c07102fc4043", "job_title": "geologist", "name": "Weatherford Labs", "photos": [], "place_id": "ChIJhSfAKyPOQIYR3TfWmiitgdk", "rating": "NA", "reference": "CmRSAAAAz4i4qja7vMqqr-7MgXyLvNpjiQgisbf0VX7AuLiIxfeEuDweRx6Lsp4Sat03vZkClRUdpLmkIa0_lBf6hsV4VKZu7e1AYmNCQxUxc5zOU-EEteWYLzijiQ5sqJPctwIGEhC4rJcYFodYjPVQ08RQyfYJGhSF4MzUPFoCZmo3ZneDIvhkQVrpCA", "types": ["school", "point_of_interest", "establishment"]}, "type": "Feature"}, {"geometry": {"coordinates": [-95.48866699999999, 29.9435503], "type": "Point"}, "properties": {"address": "4420 W Greens Rd, Houston, TX 77066, United States", "id": "a0777591ff05d81829fbccf25c638ff0202494cb", "job_title": "geologist", "name": "Weatherford Wellcat", "photos": [], "place_id": "ChIJ7aT18q_OQIYRQVu3YUEkW8E", "rating": 5, "reference": "CmRSAAAAxUu6tJCokXKCYSFkV6z-xNtg7LQJLtISQncmYKfJLKeQgCGsCZaRc-X_jZYwZXwbrIKFt0-s4ZZIYCWdWu-XFuovSqBvp0aeFQD68Niq5zvA4bCHD0fw3TNn84kXMSZyEhCWLNk4PXaZ_l52A4TUJAHSGhSPpd_MRHP_TFjXkgzre-_p3sBAQQ", "types": ["point_of_interest", "establishment"]}, "type": "Feature"}, {"geometry": {"coordinates": [-95.66870100000001, 29.786041], "type": "Point"}, "properties": {"address": "16430 Park Ten Pl, Houston, TX 77084, United States", "id": "1b41b81f14c05bef0bfa7b4b15ac1b253556cb23", "job_title": "geologist", "name": "Weatherford Us LP", "photos": [], "place_id": "ChIJK2PrHBXZQIYR5_WIovzEWWQ", "rating": "NA", "reference": "CmRRAAAA-LE8ZNBEWga1g4nl6aewEOC63X4weBuzXZfBP_ncu868gRFBpMh2d9IFiI9Vke3g45BD5Rdi3yQWSCnQ23epZp9jF256dbnkJF6ithZmGx_Za1Wicx9KVnCa7b6sVu8jEhCuoUxauaL2MdKhydWMVWaQGhS_K_q73KRVOHW0PD_rglNEyFVa7g", "types": ["point_of_interest", "establishment"]}, "type": "Feature"}, {"geometry": {"coordinates": [-95.0431184, 29.6908544], "type": "Point"}, "properties": {"address": "11931 Hwy 225, La Porte, TX 77571, United States", "id": "e655333b194bd940ac7bab961f2556d75d128a2d", "job_title": "geologist", "name": "Weatherford", "photos": [], "place_id": "ChIJRe9oNwpgP4YRQAHsNXMU0vA", "rating": "NA", "reference": "CmRSAAAA7k2EZYd-RdkoBqDHxlKFjmJo4o6xvy5_aUu-qOuggUhl0Z7xJM0C0Jz-x7wvzZZgqXY4ctp2miwkLt3uxFPcspjDJOsGV3WN_79AANShm9wMGbsAqOcKzrN44d92cBczEhDpu4kyU824d6vNeymeSSK_GhT7RsDHNde1QASe7fk8s_Tj2tg58A", "types": ["general_contractor", "point_of_interest", "establishment"]}, "type": "Feature"}, {"geometry": {"coordinates": [-95.2559629, 30.0674877], "type": "Point"}, "properties": {"address": "22001 Northpark Dr, Kingwood, TX 77339, United States", "id": "1cf42089a61995ee434212bf913c60fbc8b01cd3", "job_title": "geologist", "name": "Weatherford", "photos": [{"height": 3264, "html_attributions": ["<a href=\"https://maps.google.com/maps/contrib/116976098361550939190/photos\">Texan country75</a>"], "photo_reference": "CoQBdwAAAIexoitk8M9w2hS6zfGzOieEq3nqIbGqepUN6StOZKPJRUOHB3_4GsbEyusC780j7DfeJP3rkd5cq9oTvNwYBvmmpghqdoNmOpv5Y4d59qPrtYdsFSm88kiwfi7ql-FpHtsCDXDuAMAczg6EuCwLjEqpjAVg3tV2myUicO8t0A1SEhBAPhKzFOzN-kkqIXv1UiDOGhRcnApF5LSWVTS3gIH-ZpQf4Bf8Hg", "width": 1840}], "place_id": "ChIJ9_DxATtNR4YR5x9qO1Lvfsg", "rating": 4.5, "reference": "CmRSAAAAYUzVg2CUcygjvph7qTJvlrlgVDHSrYQJs81mrB5McbVhk5p5VGdFcbeVqO3p_ffZa_6pL-Idsb1W1vawbMGH_lK1geh5q6xNoYq8gJPtL7lfyJ7sBcb6ZQnnXzIfDeAOEhBc7gPQpaYLI8wtmI9cCxjOGhSDGKjfu8IHqW04G-wYujXKZdXj5g", "types": ["general_contractor", "car_repair", "point_of_interest", "establishment"]}, "type": "Feature"}, {"geometry": {"coordinates": [-95.35959799999999, 29.766005], "type": "Point"}, "properties": {"address": "1 Main St, Houston, TX 77002, United States", "id": "bbf863152c3e55a67956f9a69a36bfe8822bc16e", "job_title": "geologist", "name": "University of Houston-Downtown", "photos": [{"height": 2988, "html_attributions": ["<a href=\"https://maps.google.com/maps/contrib/113673164458451850004/photos\">raul medina torres</a>"], "photo_reference": "CoQBdwAAADSJgR0e_422_TiGdlxtjt1rtQXsPJgAHo8Jtx27FkSby9v8F9wdZcgCZBjPMm-Hb881HUcn9UGHrK8RSu4d-FQ14ve8MxdLF3knCcQFr_o8inw-Pz_UC1za6jXJc0BBRHrsBYrYgdiZqfyfCJQ6oKqhc4L4xO0vcWEr1A-Yfxu8EhDubUsI6D6AzipQAdeJqdDvGhQ-M-x8NTuaXAdYYyuq78OwY8DOGg", "width": 5312}], "place_id": "ChIJ0_q_Zyy_QIYRVx8D5OgE30I", "rating": 3.8, "reference": "CmRRAAAAMOVz-tXms-BIcZRPpwhfAjOeO_iXrL2_W_j9zz4TETzKaUWx6OzBHzYOoypCHfrz9kOrf5p42eUylWVMCyuTe27dSJxdU1zkzrIKQigORKGx-xbRaONwhYbWXjeG0nRoEhCXsMXGuifB2Z_7TWMndTBPGhTlBxqXuSlm3kmhnbDKoF2sbZ35xg", "types": ["university", "point_of_interest", "establishment"]}, "type": "Feature"}, {"geometry": {"coordinates": [-95.372164, 29.757501], "type": "Point"}, "properties": {"address": "333 Clay St, Houston, TX 77002, United States", "id": "795a3515ff023985c96d55d60c8eefcdc6c9ee0e", "job_title": "geologist", "name": "Jefferies", "photos": [], "place_id": "ChIJe81fkji_QIYRhzwdUhh-ygw", "rating": "NA", "reference": "CmRRAAAAc74n0EieSy54y0Clj7wfUW7a73AGlVaZwrWAMbnx0aB7NysWIV-12AVj-E6c2ODiAPHd-x08-DiTjYU0rRlv2e91i23_xzENf9_YmKJNoJlaPuONKjYBx3_o8L_eS_xcEhB7UZqFc-fWskDOunTUP-j6GhRpfk7Fc24rtkFWUtexid_ysgnQFg", "types": ["finance", "point_of_interest", "establishment"]}, "type": "Feature"}, {"geometry": {"coordinates": [-95.36392040000001, 29.7558061], "type": "Point"}, "properties": {"address": "1001 Fannin St # 1500, Houston, TX 77002, United States", "id": "f9c309a151d083c3d995d8e59499778d8c495ccd", "job_title": "geologist", "name": "Oasis Petroleum", "photos": [], "place_id": "ChIJr9ZsYDu_QIYR4jOwJRL56Zk", "rating": 5, "reference": "CmRSAAAA350wzGI1FySOvQ6o6--8GKvko4OhSxOgxQPNj_PTQ55DFo3ltUB_UVlj635N7W4y8dycF0xdWyXRL_vhKIgh2HhudcWqvHY4solXjTtwnyFlbXGCVnPpSC5mGQDDxH3sEhD-7bxyOsyiO3fKDjyCd0QIGhTjUZsk3339pBXMAKn_z6rXWTo2XA", "types": ["point_of_interest", "establishment"]}, "type": "Feature"}, {"geometry": {"coordinates": [-95.5015712, 29.7513106], "type": "Point"}, "properties": {"address": "1616 S Voss Rd #1000, Houston, TX 77057, United States", "id": "a626299a58965fab800792adff33c7961eae6309", "job_title": "geologist", "name": "Hart Energy (Oil & Gas Data Provider)", "photos": [], "place_id": "ChIJRzKfmJPDQIYRcAIeSuMCH3k", "rating": 3, "reference": "CmRRAAAAtP5aP6gYlDTy4aIe6wldihGrLMvrGsiSusxGYHHlI3seDYG_6V2PzRXUj7m7IRBFB6cgaSLQ75ODpRNDzu42X26OrF2gNcqS6bmd0Q2e7o5gbsZ1O0GOpPrLrZ4p03esEhBFAxauykFXbxf06JHe-ypBGhT_I_41KcLWmcgLyZLwF9g4tkqTfg", "types": ["point_of_interest", "establishment"]}, "type": "Feature"}, {"geometry": {"coordinates": [-95.4628465, 29.7338536], "type": "Point"}, "properties": {"address": "3050 Post Oak Blvd # 1640, Houston, TX 77056, United States", "id": "eb737b548075ce9fb5a7b7cd19dec9171f0ee698", "job_title": "geologist", "name": "Sinopec USA", "photos": [], "place_id": "ChIJS5y97nHBQIYRbb2dw19hKiM", "rating": 5, "reference": "CmRRAAAABXhns3hxbM46_NvUFHyyox1Aewhx3ILtMemu0idJoXTAF-1qDJz8eyffvyDuzeLSUEenbIOYHs6wicZhpIv8c75F1RqI3SOnb4Ocfhun2gK6m6sJVkqRTJkYe6rHMs9gEhCvkk4Z9D4dcq--frcl2Fd2GhQh8PVZqO_OO4KR0fOVmrsstj6RIA", "types": ["point_of_interest", "establishment"]}, "type": "Feature"}, {"geometry": {"coordinates": [-95.46350079999999, 29.73921199999999], "type": "Point"}, "properties": {"address": "5065 Westheimer Rd #1100, Houston, TX 77056, United States", "id": "5e9393654923a4ebf381bb69db381436c29a299f", "job_title": "geologist", "name": "Citi Private Bank", "photos": [{"height": 4030, "html_attributions": ["<a href=\"https://maps.google.com/maps/contrib/117652267326695258138/photos\">Ramesh Potti</a>"], "photo_reference": "CoQBdwAAAONZPxaMIoYvhgc0JOgRoWD1JzCGGRguCvhKqTdSp85zEHK5DYLhAEEB3xVmkN5YOehh-iaV6g3kJ2sPBkV0V-azLok-9pkRK_Yl6jn69VN4NlSPlmXdXFur2AcbV1R4a2CbqOvLA-w1YKdIUJj9t2cI7fl2Vdg8DJbHO183y9y5EhAxZ_O2pPqBx10sWqNO_wZ-GhTYHkaYbz3azHI-wuIKmPKLR3Rcag", "width": 3024}], "place_id": "ChIJFc2ux27BQIYRk9iQ3cBYcVk", "rating": 2.3, "reference": "CmRRAAAAyoTZEenQGK9IzV2qe833wGrgbh0zLWQ4eVfVptBySgqXEile5RCoXUIwmVh19ZQGGR0JJFZj-4W2Na_VPaWWiXfCktfDIOwWO9nco7-krK4zLdYAzTYkvar43dYpfKmSEhC8QzNo92jBBEqM97HefQtkGhSZnUS76w6UQxzFYkSso3vzjywxug", "types": ["point_of_interest", "establishment"]}, "type": "Feature"}, {"geometry": {"coordinates": [-95.47219989999999, 29.7496917], "type": "Point"}, "properties": {"address": "5555 San Felipe St, Houston, TX 77056, United States", "id": "23d714827e55b6e7eb16a5d356a0feb120360633", "job_title": "geologist", "name": "Marathon Oil Company", "photos": [{"height": 2988, "html_attributions": ["<a href=\"https://maps.google.com/maps/contrib/114653147413229085324/photos\">Patrick Winham</a>"], "photo_reference": "CoQBdwAAADY2mXH1lW7qDL0JANPuj02re6t4Y8MqKSnrZZt-XNbA8xCdK9mX6h1qvP1gfZihrnDmhccg2NFxR4anntR_oYJ7I50jqd57rzpf_qev7LKCcvCtPNxuby7OWSr1H-tiBsI04AmkypJ3bM1rlO8QnsrJnrwrVrNp87283a9dcZdLEhDZuinjemQ0iQmNZYXwfwwnGhSJjZvtb03xyfic4cGfJas0gBPVtA", "width": 5312}], "place_id": "ChIJieWsJFzBQIYR4INe7XAsF-g", "rating": 4.6, "reference": "CmRSAAAAV3cswHCrAwhbPwtB9qF1qyRgfbSNdf7KQj9d5XZLhFTSD7-A8M1_pvv_k_sgnBqotw8Qah9yinpqOsothYAHBIgRA8Lgmvd4G28I4cIb2ozOaLC3elhUEz27QnVYxImEEhAaJYx51Bhh1WwGhNl4WLZ3GhR5FvIB37oo1OYqH5Y8gZwXqYrJEw", "types": ["point_of_interest", "establishment"]}, "type": "Feature"}, {"geometry": {"coordinates": [-95.3699286, 29.7699427], "type": "Point"}, "properties": {"address": "PO Box 3128, Houston, TX 77253, United States", "id": "18997b37423029430e68e14ec02f1e975aa3a596", "job_title": "geologist", "name": "Marathon Oil Co: Chernosky Alvis", "photos": [], "place_id": "ChIJ64XB-DS_QIYR3wBPmVSvPQ0", "rating": "NA", "reference": "CmRRAAAAWUAEMUOoqcOk1nSaWS60Mt8wOkfRjzsm3H70fFo2ZDiNy3AQQ4hbxj_CbnUGet6LHVOYtP9OYVdCqoWBTCnWRcDtwaKzvrzE1FYdCoJC8P-3AWAuZ-ppzpWRq3reszmLEhCtyNbWeLM3ITP4S_NSVYRCGhRDuyVT1G4gG9EM_28L68GUtgAN4w", "types": ["point_of_interest", "establishment"]}, "type": "Feature"}, {"geometry": {"coordinates": [-95.3911105, 29.9585878], "type": "Point"}, "properties": {"address": "1030 Regional Park Dr, Houston, TX 77060, United States", "id": "591b862adf844e6fdf249a003d16efa649ab42b1", "job_title": "geologist", "name": "New Tech Global", "photos": [{"height": 556, "html_attributions": ["<a href=\"https://maps.google.com/maps/contrib/105073521963953436703/photos\">New Tech Global</a>"], "photo_reference": "CoQBdwAAAGPUYHv_ZCz8m4omlYnrK0JRgvUo0fxUxMSAjcwAUDG_S3NNJI47WXoHeHKJ2bxXcyWujZtY1nFFBd29e8CkdAL3IGeCbKJ4T1IlaYm7-wI8Y9Ry7AMvF24w142KycdT5rh2LSIbra93oe35Hkrc24iOQ3W2IvYFQi-GeVuziFRSEhCOwnNfg4eE2ZCN9qITQfKRGhQpz-e_0Gy6LEDRT4PcpkhtUV0ohA", "width": 1186}], "place_id": "ChIJRQuoTf61QIYRrrCBvZ7uOWs", "rating": 5, "reference": "CmRRAAAAkfKn0653AAq2C6hg3bFS1Z70wdB3u2fE5gLHlhcPbeWrs_DOEntaeM3PFPtRjC59QK0YvAzbn8vlmcFkStpXa-yA86L1nOfwUd4Mu782g5yYCzxaYvD9L-PiWYWa5HcFEhBGJSg3iQaJaE34Vh7Nf2tfGhSRjbsV5lld-N0MSoGkhBgBofWtFA", "types": ["point_of_interest", "establishment"]}, "type": "Feature"}, {"geometry": {"coordinates": [-95.4659039, 29.8679352], "type": "Point"}, "properties": {"address": "4141 Victory Dr, Houston, TX 77088, United States", "id": "90b73098291a8e90c04f33a8c85477dfcd26379d", "job_title": "geologist", "name": "Lone Star College System", "photos": [], "place_id": "ChIJqaVfqaXIQIYRf8PTc49aphc", "rating": 3, "reference": "CmRRAAAAtCwhe0PKqWt1glW5_3JXD0tjwgLHkfxH1TUneThawhq9e5LS7wSE2jdujvgTza-uyqSzBe77uHnNkPiqHXHH2ZWBf_gSVoxA-wZL6kL-3_kgfHKiP5VD4bKVY8B1e3FDEhAHdVgCOnQeq12KhuA-wflxGhR1nb2f2QSZWGVSWfFn8IDezDTfxA", "types": ["point_of_interest", "establishment"]}, "type": "Feature"}, {"geometry": {"coordinates": [-95.37974109999999, 30.007182], "type": "Point"}, "properties": {"address": "2700 W W Thorne Dr, Houston, TX 77073, United States", "id": "50e8c3703dd49384cfecda9f52ac2537c832cf50", "job_title": "geologist", "name": "Lone Star College-North Harris", "photos": [{"height": 428, "html_attributions": ["<a href=\"https://maps.google.com/maps/contrib/106036001858778134743/photos\">Lone Star College-North Harris</a>"], "photo_reference": "CoQBdwAAAL3BG4OngxKOkafHj4giftyjYQiXTRhg2ayjPlg2ubBk5tWmb7qPEecuscL8bH1oIvVP_ni5ByVeqFi78jW4l8312jgVZzmwraHR8Elk0RyoQA9VnXtUNilUVm66pFtSrOTnsmcoep2mqHGghv9ZOEW5dxp4-amoFBPKN7uh3lzNEhC_baluH4gRhR5Yo_nwe8pVGhTQak3ToUQZlsNlJ57q26_Ktc_Vpw", "width": 640}], "place_id": "ChIJFwwy8Xa1QIYRMJtJ9403tZg", "rating": 3, "reference": "CmRSAAAAPthq35X4iwi64ysBZOtfMKNRdyDJeyqViPyn3EzQaH_8ZKGQoNKbSLGlU3U9mpWqfJKt6s7S0jB0r2zp5S9qo9Q7W5LVHKFHnWkQHavZR-S2HQ2-hg3lvwlZWzR_hX9hEhDf8j1M3EOQBjHB2KAb4l13GhQsJG5a750VqxjzYbqv-qlVYK9PJQ", "types": ["point_of_interest", "establishment"]}, "type": "Feature"}, {"geometry": {"coordinates": [-95.48802210000001, 30.1872936], "type": "Point"}, "properties": {"address": "5000 Research Forest Dr, The Woodlands, TX 77381, United States", "id": "c4fbb88cbef4056a453a4e050728b4b6b1f46539", "job_title": "geologist", "name": "Lone Star College System", "photos": [{"height": 3264, "html_attributions": ["<a href=\"https://maps.google.com/maps/contrib/113764785255023487240/photos\">Victor Brazon</a>"], "photo_reference": "CoQBdwAAAN-IxcBLceBxyTzWM6KWLk15jS9_jGq9mBdx54BFWPKPWR6iBJmz73qipGUpkZZZI2V_kIc913DbG36-sFtIRbm7sB-hEpEAr-oXWvkjp1qMcq7z48tcX30Rmn4aZCtXU3hJs98XNhSsYn2IDmcuA6muVhECf51ycXVzOXXypssdEhBse2sDG6hp6XMS0zxtLcdTGhTQP7Fr9FR4kF7oSIJD4M4ZAaZC4g", "width": 2448}], "place_id": "ChIJz5LplNkwR4YRI8q2M1XhwqQ", "rating": 2.5, "reference": "CmRSAAAAlU1LhDvhqB4Q2yvgq7FPew0l8_rs3Mm7to8ZMtXvqNlCymMDc_Y2IvBBrOf02vST7nVh4UM-D5Up_IP_MQcytTc_MWw6FnPRrNxC7QRM6a52ajTfLj74P-Ps46oeXJT-EhDefvmK972PdZLsRk3GZAPIGhTOc5EcSHcq36g5Lfu2VrxdBo6kdw", "types": ["point_of_interest", "establishment"]}, "type": "Feature"}, {"geometry": {"coordinates": [-95.6012956, 29.7881337], "type": "Point"}, "properties": {"address": "12141 Wickchester Ln #200, Houston, TX 77079, United States", "id": "3cdf19db1aed68ee6eb0cb60d82ec77206b1eb4d", "job_title": "geophysicist", "name": "Geotrace Technologies Inc", "photos": [], "place_id": "ChIJE5-yOvzbQIYRJdZ1RfRAxzc", "rating": "NA", "reference": "CmRRAAAAChaQHV1AdPTv4Km5z6XZZBX8lHApJoGardEx6Z_QtDQMrB47GGa_e3jsNGWowTgeigPIxnW_IsSSoK0Sv54NivLgj1-YXGgVFTVZCij9FnF-o02JONh0H4ZMnXnlBgSCEhBIq7pNr0lLQ3rUjWCIYZeSGhQcUhVwrUVweA660F_B_HC8KMxUPw", "types": ["point_of_interest", "establishment"]}, "type": "Feature"}, {"geometry": {"coordinates": [-95.5438387, 29.7776847], "type": "Point"}, "properties": {"address": "800 Gessner Rd #170, Houston, TX 77024, United States", "id": "91282085c6930276af6f7e2abf1ee0e0fc18432c", "job_title": "geophysicist", "name": "Murray Resources", "photos": [{"height": 683, "html_attributions": ["<a href=\"https://maps.google.com/maps/contrib/106500950429449697681/photos\">Murray Resources</a>"], "photo_reference": "CoQBdwAAAImgt2YBeinBolRWpSmlrDzcMe0heRO7PsREVXkalDo2qon0OfYcJ_g6RhQbTNyGhPm-BdCDxyAKIV-Ob3wBnshV_z_YOHXPa2menY-Lx7Ra7uCi9dd_uW020-xy7AtSAI3Nwh2ET8wRpPuFV7GSx_X5qFfOoFxDKygD0e4bIEdtEhANilhLmBAKKjOhjQUt3g8tGhQHFFtZsg-o8oUe4AyQ7HADQvKhqA", "width": 1024}], "place_id": "ChIJRSYpxLzEQIYRsKFA9Ahm-Z0", "rating": 4.6, "reference": "CmRSAAAAxQTedU7_eyvjR1-YXlw05Ts8EteidP5DrDe4-7lqdXuy_P9M7tJMOekXht1agy4fyrS8a7mB94y4uA4cZK4so7y-rwhhX3ceHoON0Zq84xYDVpCpSmCcsKDkzOGvH_vdEhCazJXvSwizPpaGQN7dZs0_GhSGM0OhOxuuRuSx5nI4--lJdBV3Kg", "types": ["point_of_interest", "establishment"]}, "type": "Feature"}, {"geometry": {"coordinates": [-95.3599019, 29.7546294], "type": "Point"}, "properties": {"address": "Hess Tower, 1501 McKinney St, Houston, TX 77010, United States", "id": "04c70c4a3d18050ca437bbaedeca70bd9cb01927", "job_title": "geophysicist", "name": "Hess Corporation Exploration & Production", "photos": [{"height": 1454, "html_attributions": ["<a href=\"https://maps.google.com/maps/contrib/111482964284093817946/photos\">Sau Hei Lam</a>"], "photo_reference": "CoQBdwAAAE5-HLy2zHttUE50SckJ8MCbOk7aZALo1QQ8rsj2bQmZCSNh2GMohFSbF5VnH-3AkEum8k102xqDi-ByX0xOQkFa1HfO36jJDQz-mHaqRf8PZoiTsmwglC5CKvhbn-pExmigO82nb1W1ScGSixUt_WkgNE42vGQa3EoiBvpztBNhEhATUCRvns_JfE2pveCL95UqGhTF6Bf7H2xVHE5JYVs1WONZDOdrqg", "width": 2161}], "place_id": "ChIJfy2iBDm_QIYRjgKEE3GFL9Y", "rating": 4.4, "reference": "CmRSAAAAFQ1b8Pj1CGhfZY4dVyuIrI-gUgcr8DY-PdIeoQeqnA3I6H0RFeDvcZE0PHqf56a_6ZsEQFbGXfVOlf54_bYhEkhjY9EGsoQuzUs1xLLk2vq7JMaXlAQqSdHqTbTRqR7cEhCOu14Ryaf_U-Bcteo9op7XGhRQGlBuj8AbGVHx5sp0x3ljXyZQTA", "types": ["point_of_interest", "establishment"]}, "type": "Feature"}, {"geometry": {"coordinates": [-95.4574449, 29.6839704], "type": "Point"}, "properties": {"address": "9009 West Loop S, Houston, TX 77096, United States", "id": "2795a232d6e43ce11fa01f15cf2d6001916581de", "job_title": "geophysicist", "name": "Aramco Services Company", "photos": [], "place_id": "ChIJ4-bQE-fBQIYRMJKxqTjw_Wc", "rating": 3, "reference": "CmRRAAAAn_tYgY3I6UcgD-e-Cqa7hdUvz55YYwnm38mxet2qhOc49H5H_WDzhIDzt9MJZBOlZ65pNBMX7U4EzFNfdsnjElFNmCfnP0DNP5bNcXt9veZMMNgJDiQzlzS9Y1AFbVDHEhC8AvTqHNzEQ7ghXVllSsTJGhTdzYS2ipKFTsZ0eMswC0DN6Tlj0g", "types": ["finance", "point_of_interest", "establishment"]}, "type": "Feature"}, {"geometry": {"coordinates": [-95.4628465, 29.7338536], "type": "Point"}, "properties": {"address": "3050 Post Oak Blvd # 1640, Houston, TX 77056, United States", "id": "eb737b548075ce9fb5a7b7cd19dec9171f0ee698", "job_title": "geophysicist", "name": "Sinopec USA", "photos": [], "place_id": "ChIJS5y97nHBQIYRbb2dw19hKiM", "rating": 5, "reference": "CmRRAAAAkcYnQhM-gNwgvkq7Sv8AkEkq1LQ3fCzRILWRsFCq7dzBRs3BOKj-Q70V8QsA8eZMuDjYhyCTIbGbxFlRa_VK8SET61FSyd8VVSD6QJotS60xRvHjVeGXd_0hBvRkNzBXEhD4-FwyjbHHOJ_GqBy3iGkiGhRlcHuaodhQkboq5bvv8zXkIeNf1Q", "types": ["point_of_interest", "establishment"]}, "type": "Feature"}, {"geometry": {"coordinates": [-95.5740797, 29.7373078], "type": "Point"}, "properties": {"address": "11200 Westheimer Rd #365, Houston, TX 77042, United States", "id": "328101c9c23ad52a56a549ad72e19915b58d7af8", "job_title": "geophysicist", "name": "Walker Elliott", "photos": [], "place_id": "ChIJz6iXr8HcQIYRnzHDA7T8m-k", "rating": 3, "reference": "CmRSAAAASQdbnuXOcsbi7HNR6fGZyjdXAtX1RId1MPZ8YTIo8xvfzUhrbtJ7Ck9UjhMSZm1m-h9S0K1trJXKykT7-ng-wSySVdhcllJsk3TC_nhrm8mGuWEUqfNke5_wRzYokUJ3EhBtHFToRupL1DiCTPW0vAeBGhRne8o8I8n9fcwKFUFD_rehKF8oQQ", "types": ["point_of_interest", "establishment"]}, "type": "Feature"}, {"geometry": {"coordinates": [-95.3662701, 29.7561894], "type": "Point"}, "properties": {"address": "1111 Travis St, Houston, TX 77002, United States", "id": "6cf1f2b19f724b7014c7cab1c01725834dbc3db4", "job_title": "geophysicist", "name": "Hilcorp Energy Co", "photos": [{"height": 2448, "html_attributions": ["<a href=\"https://maps.google.com/maps/contrib/100318015046809414765/photos\">Ronald Payne</a>"], "photo_reference": "CoQBdwAAAJM5cVOcQp0Kb3rfpnCEs6z-jLYsN248MKcrETKt6KO4QMT_qg7HRd3LspjapAEoZRuW1Tg0cljQnA5TTrHMk-Y1oDkkEQI703p4scDbNrCJYLdrM5gsIbAZIiyBSNaYZqzmX9yJSnjG6felhj5d1CKG5b9VwylRxUNbne8izQAAEhC3TNrrwU-q7VxrYRO-pbs6GhSOETAyUn_BSeHDbTBaKmUSA4q26g", "width": 3264}], "place_id": "ChIJncGsRDm_QIYR0e57PbvugTc", "rating": 4, "reference": "CmRRAAAAbXcyb5TAJfk9l2O99SwgBGSAn6fPr2Jcnx8b4GrxaSghkFIEG41mrYeTblUwgsIsE7s4jbY65FEn_oj9m26me2n1IzbfG5vbFgNi2WrWoV_t09mJ6Rm8GrQpts7rqkQVEhCA-0OabtSChjx7I6oh2TpcGhRCcgh4kVYgByjO4g7jB9_IQflPwA", "types": ["general_contractor", "point_of_interest", "establishment"]}, "type": "Feature"}, {"geometry": {"coordinates": [-95.4321022, 29.7305064], "type": "Point"}, "properties": {"address": "5 Greenway Plaza Suite 110, Houston, TX 77046, United States", "id": "7394562c1f1a87dc4b6fa017b44a961df160f5ef", "job_title": "geophysicist", "name": "Occidental Petroleum Corp", "photos": [], "place_id": "ChIJjd5k24G8woAREjjHjBsq0Yk", "rating": 4, "reference": "CmRSAAAAeO8MlWjtXfgudEfdIFtcNcseM3hQ3gAG-FXEUfCzlragR-0dmtRoBJpKVT_0INhPmXDLZBDIuOu278vYhVtGy8kjCKFuGeIHtrqfUtx02IeRF5SeST6-139uIM5GJOosEhAnZZNz1YMGss-KQF1jWbO3GhQOacccCqq6TIKb6WhUFExEcCuEWg", "types": ["point_of_interest", "establishment"]}, "type": "Feature"}, {"geometry": {"coordinates": [-95.3970411, 29.9417677], "type": "Point"}, "properties": {"address": "363 North Sam Houston Pkwy E, Houston, TX 77060, United States", "id": "bcfc0554855f942f730466fd447878511b6aa0b4", "job_title": "geophysicist", "name": "Occidental Petroleum Corporation", "photos": [], "place_id": "ChIJx73rqePJQIYRPjss3jFElZo", "rating": "NA", "reference": "CmRSAAAASs2o2jmOViF1UKai7eRaqF7Ao2Sx755gwAN2tozs6HskmyKcJVBK8kt-cP8luiVz1QAyUM7pVUffdAWdjUiQo-aYAsNJvlqOeiBkrQaExP6gni4XB0o3gtsmQ2PNZl_bEhBfsMr48SIo7F05vxdXqOVkGhQZXBTwQxeTcq7cRsTIfNTkM-yehQ", "types": ["point_of_interest", "establishment"]}, "type": "Feature"}, {"geometry": {"coordinates": [-95.5498597, 29.66888299999999], "type": "Point"}, "properties": {"address": "4301 Southwest Fwy, Houston, TX 77027, United States", "id": "6e40f1d16226178cc0cf90f68d007ada7cfe5617", "job_title": "geophysicist", "name": "Oxy USA Inc", "photos": [], "place_id": "ChIJj7uu3g7BQIYR1FyPVqiuar8", "rating": 1, "reference": "CmRSAAAAFVF8CDT9ZRdBB1wRM7wS3u3iqvjbVsDc2VRTwpCZ5w0Xl-P5FmThK_DUmUpyJgAuoecG2ojHvK31KIH-05v9aT5PeayZFVlbmFIP2-ulL5x_J0lhYix4qwDdgaa7B_TPEhDpVdeexXE-OhFuz3OgC6QjGhSZH-W_TEqXmC_tRmtqUeKGdxyptw", "types": ["gas_station", "car_repair", "point_of_interest", "establishment"]}, "type": "Feature"}, {"geometry": {"coordinates": [-95.362117, 29.76005199999999], "type": "Point"}, "properties": {"address": "1001 Texas Ave #1020, Houston, TX 77002, United States", "id": "a11c06170d12ee3b5509eebe23f7a83e021bcdac", "job_title": "geophysicist", "name": "Lumina", "photos": [{"height": 808, "html_attributions": ["<a href=\"https://maps.google.com/maps/contrib/104809654983163322864/photos\">Lumina</a>"], "photo_reference": "CoQBdwAAAHJ_vDmxVDLOITlR-esaqsd5odeGq71SVTc3ALw4kjXJTYeAlzqwficxoOloOUr43u7OaIofHrqe9XKiViVIf-79DJG_CUNa6_ghsNjtBAybM_30ies8aHehc4EY5Q1pfyTT2bnXYlB3SJ3szwWjRFe4yEok7trkBPjnhEg0ogtLEhCBdUojx9qiDbk-Rj5jgmFQGhTF4NfsQL4TZWLv89hwehx6VrkOtA", "width": 1024}], "place_id": "ChIJiUNxO0C_QIYRfHaVr4rYzPY", "rating": "NA", "reference": "CmRSAAAA0teO86yzS3LertZN4YF80vBPAucaBPHixY_jwzLwQau8YVJ6dHHrsmuMzXVicKARRlAR1vHJ6SUqzvapexUlb2anuNUMkfGcTV4UixJ6jD-u86gw0SlZKUQebQPA9N33EhBfI6WIYWv2E7cuIVRaRX6oGhQlZ1m8AhrAVPho_dxpiC0Bp3xiMA", "types": ["point_of_interest", "establishment"]}, "type": "Feature"}, {"geometry": {"coordinates": [-95.451906, 29.754584], "type": "Point"}, "properties": {"address": "50 Briar Hollow Ln, Houston, TX 77027, United States", "id": "7e34dad551ed799d5f99931250df058f8447acc9", "job_title": "geophysicist", "name": "Integrated Geophysics", "photos": [{"height": 1360, "html_attributions": ["<a href=\"https://maps.google.com/maps/contrib/118046956100093733952/photos\">Integrated Geophysics</a>"], "photo_reference": "CoQBdwAAAP0BXCJblHnpXV9MxVztwT8bGO0Zv85UexyMYUlamP63ASNX5RVP6M7KTe0aW8XUbz_oRFK3nJS8lAQuDCz2Oiu44MjIDNygcQqN7iidFleoN2B6fGvjx2ThDcDU7oEeWZ4GohxO48vRQF_rrXLi2wvZX5zu8_rxxQ4PALCmlgGQEhDU3WCuQMIs6XKN4EBeaxOxGhQxLV_EVeMyuKVfK_7nqV6lBYvUKg", "width": 1359}], "place_id": "ChIJvbQlyTvBQIYRm0AeqK4g8R8", "rating": "NA", "reference": "CmRRAAAAnS6AraEsMe86ms17YRPD6TRrNiFLreHbP0kJDhLByYQfUJV7RfkKeWK_w6G_hFkKzSxocL4Ye3s1rWeNvo1x0YVRnirSQ6tyuONcfv44a3VdQ01hmAJGsZGyfLNV7CiaEhAFZ8vCBzi0PBhUnZNtNjP6GhQiS6tlkJbqbvzEQIPz4Pmdq8ePkA", "types": ["point_of_interest", "establishment"]}, "type": "Feature"}, {"geometry": {"coordinates": [-95.4628465, 29.7338536], "type": "Point"}, "properties": {"address": "3050 Post Oak Blvd # 1640, Houston, TX 77056, United States", "id": "eb737b548075ce9fb5a7b7cd19dec9171f0ee698", "job_title": "geophysicist", "name": "Sinopec USA", "photos": [], "place_id": "ChIJS5y97nHBQIYRbb2dw19hKiM", "rating": 5, "reference": "CmRRAAAAKR1qf1CSfOUmYe5hM3ayoOTrl8-rKAJXLOReULFSVK785_7hHgcA8z0HHvosCEMlKFAEZnbvgZvGAKx0AnCWvfyQiIF1TMNApQkGSEW-krlo4BU5tX61KXLVUwXv0HXiEhAgMr8L416_kyhqFzM9NvaiGhS-HWghz0UROsZ2RWjoB6R5JxUsag", "types": ["point_of_interest", "establishment"]}, "type": "Feature"}, {"geometry": {"coordinates": [-95.62566849999999, 29.7794433], "type": "Point"}, "properties": {"address": "15375 Memorial Dr, Houston, TX 77079, United States", "id": "63e8846758150bbb7b96bb6f1b6575612bdc5048", "job_title": "geophysicist", "name": "PGS", "photos": [], "place_id": "ChIJ_Yxnp-zbQIYRwzVN-oronfk", "rating": "NA", "reference": "CmRSAAAART_c1MGvULr9wrcFbae-b0gMrLDkJ2h0l4i24nFTm8HocR2vDlBqoQSYy1c5cyo17OgkJp_s7_xBmatujTkZ3hfq431c5-0GYLojMbh8SccHHHz4E5T7BCCuSt0-3FJLEhBiiKs6Lr1Ot6xLyX2cXousGhQfYeF3i7opKe09iGelLOB3y-st4Q", "types": ["point_of_interest", "establishment"]}, "type": "Feature"}]

In [275]:
copied_feature_Collection = FeatureCollection(copied_feature_list)

{"features": [{"geometry": {"coordinates": [-95.46103649999999, 29.737203], "type": "Point"}, "properties": {"address": "2800 Post Oak Blvd #3900, Houston, TX 77056, United States", "id": "4b62e79323dd04edd16f18a3570c6c525c72352a", "job_title": "geologist", "name": "RBC Capital Markets", "photos": [], "place_id": "ChIJMzyxy23BQIYRmQh7_lj7cok", "rating": "NA", "reference": "CmRSAAAAZHCxUrcoNdmNHk-acO8JGRqvdpVGfoaJwc8gocBrMOwPY_kNrdG_voVRQhyobLytDJDE3z4no1B-jG-S1UU-XT65b8VH-a4MgXx5-b2DqbRErnd959mCH-Gbr5Bu7ptNEhA-to4Cld2aG366VDyB5m5RGhSDRAL2FObJKSL8ZwimNGfoWI8D1w", "types": ["bank", "finance", "point_of_interest", "establishment"]}, "type": "Feature"}, {"geometry": {"coordinates": [-95.3640089, 29.7604054], "type": "Point"}, "properties": {"address": "600 Travis St # 6500, Houston, TX 77002, United States", "id": "e6f1fffeaff13624b25a14bca2c17e581e517245", "job_title": "geologist", "name": "Royal Bank of Scotland", "photos": [], "place_id": "ChIJa0oElDq_QIYRxrrhsSUehHU", "rating": "NA", "

In [274]:
convertFeatureCollectionToGeoJSON(copied_feature_Collection,"../DATA/test_geojson_Everything_byHand_v2.geojson")

got to the function convertFeatureCollectionToGeoJSON


In [233]:
#### Two user supplied arguments
###### company_list_formatted = company_array_formatted
###### path = '../DATA/test_geojson_gAndg_v5'

make_geojson_from_CompanyJobList(company_list_formatted = company_array_formatted,path="../DATA/test_geojson_gAndg_v6.geojson",geographic_limits = geographic_limits)


job_title put into googleAPI call is = geologist
array_of_features =  [{"geometry": {"coordinates": [-95.46103649999999, 29.737203], "type": "Point"}, "properties": {"address": "2800 Post Oak Blvd #3900, Houston, TX 77056, United States", "id": "4b62e79323dd04edd16f18a3570c6c525c72352a", "job_title": "geologist", "name": "RBC Capital Markets", "photos": [], "place_id": "ChIJMzyxy23BQIYRmQh7_lj7cok", "rating": "NA", "reference": "CmRSAAAADuTV9QxW4KU1_EKpjj5ebTgzwkdDUESQitwdpp9YfgfYYRUSmFyfRPEeoZwSqmgjWzdxPFYGiUL6k5e-0m4zWCGeqij11FgFZ4f_lLekIL-UlGRNHi4xlScsOvL7-oAxEhAk9wNIaYp8Mmli3utI9Rc-GhRpp43ZIhrplKcv3GRQqrNQuMjKiA", "types": ["bank", "finance", "point_of_interest", "establishment"]}, "type": "Feature"}, {"geometry": {"coordinates": [-95.3640089, 29.7604054], "type": "Point"}, "properties": {"address": "600 Travis St # 6500, Houston, TX 77002, United States", "id": "e6f1fffeaff13624b25a14bca2c17e581e517245", "job_title": "geologist", "name": "Royal Bank of Scotland", "photos": [], "pl